In [1]:
import torch
import pickle
import random
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F
import torch_geometric.nn as gnn
import matplotlib.pyplot as plt

from torch.utils.data import Dataset, DataLoader, random_split
from sklearn.model_selection import train_test_split
from torch_geometric.data import Data

In [2]:
from net import PSOGNN
from oripso import OriPSO 
from base_function import *

In [3]:
splited_path = r'A:\Code\deepso\splited_data_no.pkl'
with open(splited_path, 'rb') as f:
    dataset = pickle.load(f)


In [4]:
train_set = dataset['train']
test_set = dataset['test']

In [5]:
print(torch.cuda.is_available()) 

True


In [6]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
use_amp = torch.cuda.is_available() 

In [7]:
import torch
import matplotlib.pyplot as plt
import time  

def test_pso(test_set, pop_size=100, dim=10, lower_bound=0, upper_bound=1, W=0.5, C1=1.5, C2=1.5, max_iter=100, device=device):
    
    start_time = time.time() 
    function_losses = []
    total_loss = 0
    function_count = 0

    for func in test_set:
        dim = func['dim']
        func_type = func['func_type']
        params = func['params']

        def function(x):
            function_instance = Function.get_function(func_type, x, params)
            return function_instance.evaluate_function()

        X = torch.rand(pop_size, dim) * (upper_bound - lower_bound) + lower_bound

        pso = OriPSO(pop_size, function, dim, lower_bound, 
                     upper_bound, W, C1, C2, X, device, max_iter=max_iter)

        G, global_best, mean_fitness = pso.run()

        loss = mean_fitness

        function_losses.append(loss.item())
        total_loss += loss.item()
        function_count += 1

        if torch.isinf(torch.tensor(total_loss)) or torch.isnan(torch.tensor(total_loss)):
            print(f"Warning: Loss is {'-inf' if torch.isinf(torch.tensor(total_loss)) else 'NaN'}")
            return function_losses, None, None 

    avg_loss = total_loss / function_count if function_count > 0 else 0

    end_time = time.time()  
    total_time = end_time - start_time  

    return function_losses, avg_loss, total_time

function_losses, avg_loss, total_time = test_pso(test_set, max_iter=200)

print(f"Average loss across all functions: {avg_loss:.4f}")
print(f"Total runtime: {total_time:.2f} seconds")


Average loss across all functions: 29.6285
Total runtime: 10650.10 seconds


Average loss across all functions: 29.7958
Total runtime: 7417.58 seconds


avg loss = 152

In [8]:
print("Function losses:", function_losses)
print(f"Average loss across all functions: {avg_loss:.4f}")
print(f"Total runtime: {total_time:.2f} seconds")

Function losses: [9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367

Function losses: [9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 5.9604643443123e-10, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 5.9604643443123e-10, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 4.542767292165743e-15, 5.0867077104534576e-15, 1.4800125372211453e-14, 8.93857267391697e-15, 1.4539120639844513e-14, 8.064408414329167e-15, 1.2196530745534236e-14, 7.999224146840265e-15, 4.297981546672828e-15, 8.715585321321644e-15, 1.4118252838243427e-14, 5.436130824052485e-15, 1.076252090649165e-14, 1.0245688507131388e-14, 1.1233366193079582e-14, 9.141942743453885e-15, 1.348433930974894e-14, 4.1642422440814255e-15, 8.560593538567158e-15, 7.509999092329862e-15, 8.431203326643433e-15, 1.1305055673603397e-14, 6.993701170759318e-15, 1.3002606261657002e-14, 5.264648156847905e-15, 1.1266571578677845e-14, 1.3151534982575042e-14, 1.0095695912831597e-14, 4.7950793489114855e-15, 6.593207899671487e-15, 9.085199159284373e-15, 1.361767669520687e-14, 4.122925670980255e-15, 1.1972083108137844e-14, 1.271178004031608e-14, 1.2097482100814107e-14, 5.647756076693341e-15, 1.215711322030081e-14, 7.251968292640732e-15, 4.772286115817346e-15, 6.291091999693086e-15, 8.743658534292494e-15, 4.025298771062093e-15, 8.990389914465251e-15, 4.317994817634079e-15, 7.402364921656364e-15, 5.335911579799251e-15, 1.3530506840539035e-14, 5.726400121230588e-15, 3.9982148925736365e-15, 4.474496013100572e-15, 8.617726757892408e-15, 1.4129285442381415e-14, 1.4732650727633176e-14, 8.200712109168382e-15, 1.1535024271749992e-14, 9.455645630634252e-15, 1.1847855562027634e-14, 1.5001753094975867e-14, 5.1086678866439725e-15, 1.3705980726991078e-14, 1.5205776226915116e-14, 4.999958831160408e-15, 7.080502142578623e-15, 1.2907719089806733e-14, 5.821643046918703e-15, 4.049268956436442e-15, 5.730087679166459e-15, 7.695464579427717e-15, 1.3363695560038562e-14, 9.558582156582278e-15, 7.574628553238313e-15, 3.999862371656046e-15, 1.2974306890889235e-14, 7.219377005929228e-15, 4.275682557303411e-15, 9.249088176116818e-15, 3.944479122399824e-15, 1.3105766404303103e-14, 1.342444815114743e-14, 1.3763365515101662e-14, 1.3700102318337133e-14, 7.360237738024671e-15, 7.04781048246287e-15, 1.0949535616850033e-14, 1.5105219863548874e-14, 6.9253028367520595e-15, 1.3096299117051641e-14, 1.1951649285318281e-14, 9.080476103570483e-15, 1.1595394850999648e-14, 8.565415697135877e-15, 7.402429296160355e-15, 1.1152014607726437e-14, 1.1607824212467657e-14, 1.1009314967102505e-14, 7.517579190174841e-15, 1.5272168363386802e-14, 4.3056615944055826e-15, 1.074133068325019e-14, 5.339247195545538e-15, 1.4233145234241948e-14, 4.54579585846865e-15, 1.0852683328562134e-14, 8.091533797432039e-15, 1.27424070576229e-14, 1.270812085798394e-14, 1.0058201999421385e-14, 9.206233391183434e-15, 1.1643190379114366e-14, 1.0977153973128206e-14, 4.183743483626061e-15, 7.870193923919123e-15, 1.3988486543691121e-14, 6.859705640701371e-15, 1.1834126852018536e-14, 1.1980777054308462e-14, 9.396463438609594e-15, 1.3948454919570936e-14, 1.5078707732299815e-14, 3.928416413104567e-15, 9.816101348371267e-15, 9.04867425156582e-15, 7.163030680211978e-15, 9.614222903854466e-15, 3.83215281271501e-15, 1.4432856968479672e-14, 1.0086614872604083e-14, 1.203858620592562e-14, 9.687426032255024e-15, 1.2375979757607743e-14, 7.175883558153615e-15, 1.4412086026547102e-14, 1.4584973921411178e-14, 6.152564419850855e-15, 1.2519557771397977e-14, 1.0798486772465015e-14, 1.3609696797810787e-14, 5.342310490199283e-15, 1.2090273850432973e-14, 5.6237147405514224e-15, 7.552227072882278e-15, 9.437281109304831e-15, 8.851282540570625e-15, 4.285082505435566e-15, 9.122571946983127e-15, 6.889365346382428e-15, 7.141570253460343e-15, 1.2073007083803194e-14, 1.0307310154044139e-14, 8.757566815286409e-15, 9.06529303799095e-15, 4.968968013202742e-15, 5.462042408941941e-15, 7.764856906598578e-15, 1.2350426467654975e-14, 7.53506195020617e-15, 9.202170174135455e-15, 8.771770710778917e-15, 4.115226988522661e-15, 1.2800298371435943e-14, 9.390389365344833e-15, 8.291321764635016e-15, 5.871269013232438e-15, 1.3496315508590168e-14, 7.095564082446699e-15, 8.847911349440553e-15, 1.095865562059312e-14, 6.274433826235909e-15, 1.2156289057243131e-14, 7.84590101899187e-15, 9.315389680063148e-15, 9.876218664769693e-15, 5.500159738601332e-15, 7.480799325539165e-15, 8.306876677678394e-15, 7.73453736225161e-15, 1.3893091999105447e-14, 1.2389513650038972e-14, 1.1501476684841038e-14, 1.0226431213075562e-14, 7.691742716657481e-15, 1.4126214947947618e-14, 5.220117093711904e-15, 6.0843113519940505e-15, 7.141842151036411e-15, 4.724122975403519e-15, 9.990582512209127e-15, 1.3271580727024657e-14, 1.1462868923105187e-14, 5.784726809978519e-15, 1.3653412168218582e-14, 8.438393789332675e-15, 4.3659762694807196e-15, 7.165632765425943e-15, 8.258311196614621e-15, 1.1887201089460543e-14, 8.111289993893798e-15, 6.578881184401628e-15, 9.015901699803604e-15, 1.0621229881659002e-14, 1.2754382409431182e-14, 6.5780815852994196e-15, 1.4272086726959017e-14, 5.703999911423974e-15, 1.1165129218848775e-14, 1.084464837402448e-14, 1.1933557508597877e-14, 3.834481306287012e-15, 1.49875517405822e-14, 8.654637912634908e-15, 9.759027421352325e-15, 1.4733048833118385e-14, 9.726831699027189e-15, 7.583771426870976e-15, 1.459151301576398e-14, 1.1872080704319107e-14, 5.313649859879513e-15, 1.1885318982251744e-14, 1.0094867514609182e-14, 1.0089630309896309e-14, 8.205468199167214e-15, 9.315063572378456e-15, 4.0933739619999736e-15, 1.0772934329545195e-14, 1.4847833655932605e-14, 1.1357812273690183e-14, 1.4904659402298e-14, 5.444251328917812e-15, 7.773991309901768e-15, 5.6207488546866115e-15, 1.319831576521895e-14, 6.261684709830311e-15, 4.209013017541499e-15, 1.0160325373740047e-14, 1.143516501649934e-14, 1.4526040757073012e-14, 7.251233068042515e-15, 4.0928754831105144e-15, 1.1216511084462168e-14, 1.4128444338664791e-14, 1.4666861678619934e-14, 1.3408748395470071e-14, 4.686686236717247e-15, 7.2065368334818e-15, 9.67022872232692e-15, 3.875827102024863e-15, 1.0004074900025941e-14, 9.291688004133079e-15, 8.12123500772751e-15, 9.900533592553575e-15, 5.991919962722867e-15, 1.0580912807435592e-14, 1.2554613923985991e-14, 1.0101038996662877e-14, 4.671565428059337e-15, 4.545067410134012e-15, 7.584493945974984e-15, 1.1960355089950161e-14, 7.817924367777007e-15, 4.4982802747429995e-15, 9.434117441246836e-15, 6.253238944313238e-15, 1.1668890205767009e-14, 8.56932644825335e-15, 4.182854522547918e-15, 5.650505969156602e-15, 1.0600747777961446e-14, 7.233794353724444e-15, 7.454104235173498e-15, 1.2543312810403724e-14, 1.2423987043959275e-14, 4.962148550944397e-15, 1.2926959443203614e-14, 6.1785844249575596e-15, 1.0708689421594798e-14, 1.1690547144162407e-14, 1.3795728949950355e-14, 1.4684915338857712e-14, 6.730977385025925e-15, 5.776203964463246e-15, 1.2670011151621075e-14, 1.2783750735778383e-14, 1.1906206814731035e-14, 1.276832372471004e-14, 7.476124550703268e-15, 9.41880901479111e-15, 9.66861851269419e-15, 7.593381015657576e-15, 7.300707415458692e-15, 9.312746090234768e-15, 5.2768738068921e-15, 1.3652995428008532e-14, 9.718285136589393e-15, 6.3026963510704696e-15, 7.671099676699947e-15, 1.526147711352656e-14, 1.31292588630952e-14, 1.0195958355765141e-14, 8.205952702013044e-15, 0.0, 0.0, 0.0, 0.0, 0.0, 1.1211497783660889, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 5.9604643443123e-10, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 5.9604643443123e-10, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 3.9448835806321376e-15, 1.3863896467479486e-14, 5.8700950255675434e-15, 1.1716421459602184e-14, 4.321478664146136e-15, 1.423575409571949e-14, 9.05493975427666e-15, 7.45830213046009e-15, 1.105225276126472e-14, 7.29851783529004e-15, 7.305041683049792e-15, 1.1203410872899933e-14, 8.467641837001365e-15, 1.424260320413099e-14, 1.3047956405652997e-14, 1.2842309511553861e-14, 9.786806713890477e-15, 1.0233556454227865e-14, 1.4933804111947127e-14, 1.39244186656267e-14, 5.9480419619891995e-15, 5.634793931501509e-15, 1.093003353027245e-14, 7.209889389887033e-15, 1.05027994290398e-14, 6.5291781380896925e-15, 4.838095917137795e-15, 1.0205850853556124e-14, 8.99664355871483e-15, 7.830104701558524e-15, 5.465705826438816e-15, 7.758956475088005e-15, 1.1106210454070713e-14, 4.258963820990506e-15, 1.0259520555160051e-14, 1.4686572135302542e-14, 4.167882368172251e-15, 1.1613773771889171e-14, 1.22625747514646e-14, 4.5614710501905385e-15, 5.258365289961646e-15, 4.863357827756707e-15, 6.661715500928941e-15, 9.16865053931376e-15, 8.108508337695015e-15, 4.923187999986015e-15, 7.365301300983357e-15, 1.4526237268716775e-14, 1.062515164420479e-14, 7.463511383085705e-15, 4.4554775823358716e-15, 9.717066256178294e-15, 1.0831177162031348e-14, 1.1961937347495632e-14, 1.3697948313552265e-14, 4.4684278690664426e-15, 6.9903824956719755e-15, 7.598185386534402e-15, 5.642762817469277e-15, 1.1635700913794744e-14, 1.477741472482967e-14, 3.9083387676393244e-15, 8.123725284592438e-15, 1.2429912886458266e-14, 6.660266227556189e-15, 1.0941650587144042e-14, 9.589640313659251e-15, 4.734920951415117e-15, 1.1811492437602007e-14, 6.9526721653437405e-15, 4.7399023521779195e-15, 1.1478384872632991e-14, 8.138379801612885e-15, 8.620571094529288e-15, 1.2041200996633795e-14, 1.3428089545787676e-14, 1.2570179001424736e-14, 4.148837679386185e-15, 1.4769833779951745e-14, 1.2287938306037183e-14, 9.612967601026635e-15, 4.829230446795358e-15, 8.505284828210294e-15, 9.498127721070844e-15, 1.4128149571199147e-14, 7.312397317163748e-15, 1.1596271530100056e-14, 6.111348220153934e-15, 5.86419459405697e-15, 1.5105133466188254e-14, 7.175878475955931e-15, 1.0395629432421397e-14, 5.797899866374218e-15, 9.230763465335919e-15, 1.3294213447375292e-14, 9.652572320541404e-15, 5.992714903143865e-15, 9.342364291301409e-15, 8.146130153080262e-15, 3.948791790650769e-15, 1.3902722763715729e-14, 1.3323098964942558e-14, 7.694670062523192e-15, 1.0402392990505223e-14, 8.347741782218678e-15, 4.441340178929724e-15, 6.2742572198664064e-15, 5.759813029900928e-15, 7.0617119871932074e-15, 5.608842112547058e-15, 1.3504738404217665e-14, 9.88791449570538e-15, 4.397800991374958e-15, 1.0248913161561585e-14, 5.568623717662003e-15, 1.5047948577853222e-14, 6.964296421995385e-15, 1.1578444874692142e-14, 8.915794263899407e-15, 4.335673242276223e-15, 4.204841380276271e-15, 8.636742647558267e-15, 1.1146740980596832e-14, 1.0465328385519165e-14, 1.4240223041549205e-14, 1.4810305014171556e-14, 5.424704773110498e-15, 3.923623900689002e-15, 8.04437693215955e-15, 7.138739469350619e-15, 4.307622475678476e-15, 1.3717388566724699e-14, 1.0464976866846054e-14, 1.2206860312326002e-14, 1.3358549834883993e-14, 1.0030051706452336e-14, 5.739204718294231e-15, 9.503602942041896e-15, 1.3823927523797398e-14, 9.942637059262745e-15, 1.2433916811199937e-14, 6.742559290030207e-15, 8.362619068904252e-15, 9.26268898415088e-15, 4.298665949294209e-15, 1.2607293444074578e-14, 5.342215198992717e-15, 6.974603118897575e-15, 1.0899783442627157e-14, 9.638775847896526e-15, 1.0109590641298356e-14, 1.4243368921915307e-14, 8.120238049948592e-15, 9.381969857849125e-15, 6.5433905039116724e-15, 8.505652440509402e-15, 1.4985888167873794e-14, 7.111557335040281e-15, 1.0314075406193859e-14, 1.196042624071773e-14, 5.900933801111178e-15, 1.3351342431535806e-14, 5.317367487485012e-15, 7.821811401971957e-15, 1.2969040887056155e-14, 9.59853161850658e-15, 9.918483067738841e-15, 1.0987790165846879e-14, 1.4825309355799218e-14, 9.95245163002258e-15, 1.285927727555326e-14, 1.3814040955237045e-14, 1.3950403942382568e-14, 3.8784728094356114e-15, 1.3068907765603332e-14, 1.287750288347933e-14, 9.378942562095639e-15, 9.162867845382856e-15, 6.3765690590158325e-15, 8.249654519893682e-15, 1.0085192704285643e-14, 1.3781791869836232e-14, 1.2643739577729036e-14, 9.485926211465646e-15, 1.1988521476545208e-14, 9.903334730510145e-15, 1.2052823982736018e-14, 1.2908306930672128e-14, 1.4396478597460995e-14, 1.3581824331648437e-14, 1.3200599366044747e-14, 7.448009833118004e-15, 7.672170326345276e-15, 7.676812913929177e-15, 8.062574587998361e-15, 1.2033486220550203e-14, 8.743654299127757e-15, 1.0153354292584144e-14, 1.3368477061025813e-14, 7.123299752788068e-15, 4.542295918330596e-15, 9.300942686114779e-15, 1.2992933145399357e-14, 1.1401774130685629e-14, 8.157852242037314e-15, 9.6688929513691e-15, 6.486019268328244e-15, 1.1467128651796929e-14, 6.9725820982854264e-15, 5.768556951015434e-15, 9.2830126926873e-15, 4.2173473982260075e-15, 1.2246542111838971e-14, 6.078080154117574e-15, 5.281592627441253e-15, 1.030458270795398e-14, 4.175272307120571e-15, 5.45662563324425e-15, 4.085232704827439e-15, 1.0614185108636688e-14, 6.558211039389781e-15, 4.9991634672229366e-15, 6.217220562297144e-15, 3.89735317382991e-15, 1.2461047276500492e-14, 1.325664584209867e-14, 1.2581164171717677e-14, 1.2079167554428574e-14, 7.149944868209846e-15, 1.4192459700686482e-14, 5.832654475233009e-15, 1.1531044910963791e-14, 1.3591603327024488e-14, 1.0086818160511424e-14, 1.0916372582899132e-14, 4.094671616475167e-15, 7.591859744484307e-15, 8.709349464763958e-15, 1.0807162083910794e-14, 5.68426531430237e-15, 7.539552071859565e-15, 1.3236239971366366e-14, 1.0462311254161045e-14, 1.1499900356526198e-14, 1.0632160841843319e-14, 1.1822415774489798e-14, 1.2944009369398896e-14, 1.0541539327915423e-14, 9.344534389712274e-15, 8.976341873035039e-15, 1.4416793835667942e-14, 8.044696263580665e-15, 8.7744752869795e-15, 7.221883376420154e-15, 5.710220944905083e-15, 6.279223797552632e-15, 1.3158849112074582e-14, 6.794236346625718e-15, 9.07159242201968e-15, 9.554773049418475e-15, 1.4479719913319464e-14, 9.685772623941984e-15, 5.969281313141601e-15, 1.4947578561735377e-14, 7.57197649308046e-15, 1.3681814029972966e-14, 6.17187295939999e-15, 4.7525515186957416e-15, 1.2450556773448748e-14, 1.3761695166129677e-14, 8.311361717134105e-15, 4.456934055488675e-15, 6.549822448596648e-15, 9.550257516776663e-15, 5.655548779808081e-15, 5.790980030711624e-15, 7.499221445108999e-15, 7.194603833320882e-15, 8.229791597280569e-15, 1.2970558770097635e-14, 6.091433628531038e-15, 1.1546150049512177e-14, 1.0744859422508451e-14, 5.357513884569551e-15, 6.6251711114526015e-15, 1.2143380275126976e-14, 5.705165428759396e-15, 1.3443555520371592e-14, 1.0360219220061431e-14, 5.7405294778237366e-15, 1.3048491730475661e-14, 8.699527270707597e-15, 7.890468504544602e-15, 1.3509238690266427e-14, 5.209360198798248e-15, 1.2724781996056433e-14, 1.453771795328386e-14, 1.0101426090719772e-14, 4.7944262865091524e-15, 6.862474167889472e-15, 0.0, 0.7263364195823669, 1.840303659439087, 1.8942551612854004, 0.0, 0.0, 0.0, 0.0, 0.989266037940979, 0.7673504948616028, 0.9333093762397766, 0.0, 0.922321617603302, 0.0, 0.7522371411323547, 0.0, 0.0, 0.0, 0.8923279643058777, 0.0, 0.0, 0.8875262141227722, 0.0, 0.8928304314613342, 3.2074830532073975, 0.0, 0.0, 0.0, 1.9617042541503906, 0.0, 1.1165046691894531, 1.0369625091552734, 0.8292117714881897, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.680812418460846, 0.0, 0.0, 0.0, 0.0, 0.9112669229507446, 0.8429248332977295, 0.0, 0.8167577385902405, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.6125091314315796, 0.8603945970535278, 0.0, 0.8148428201675415, 1.6427931785583496, 0.0, 1.3427777290344238, 0.0, 0.8451746702194214, 0.7465373873710632, 0.0, 0.0, 0.0, 0.0, 1.3807226419448853, 0.0, 1.4095067977905273, 0.0, 1.0239731073379517, 0.0, 0.0, 0.0, 0.0, 1.0012211799621582, 0.0, 1.3872566223144531, 0.9696323871612549, 0.898273229598999, 0.0, 0.0, 0.0, 0.0, 0.7630326747894287, 0.0, 0.0, 0.8177956342697144, 0.0, 0.9021456837654114, 0.0, 0.0, 0.0, 0.0, 1.4663833379745483, 1.0768241882324219, 0.0, 0.6828454732894897, 0.0, 0.9138219356536865, 1.3864375352859497, 0.7246692776679993, 0.0, 0.7496607899665833, 0.0, 1.3972628116607666, 0.0, 0.0, 0.0, 0.6948904991149902, 0.0, 0.0, 0.0, 0.0, 1.4169129133224487, 0.0, 0.0, 0.0, 0.8563793897628784, 0.0, 0.7506063580513, 0.7746662497520447, 0.0, 0.0, 0.8751681447029114, 0.0, 0.0, 1.4624038934707642, 0.0, 0.0, 0.0, 0.0, 0.8272561430931091, 1.4943885803222656, 0.0, 0.0, 0.8118939995765686, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.9938600063323975, 0.0, 0.7532002925872803, 0.0, 0.0, 0.8176791667938232, 0.0, 0.0, 0.0, 0.7639613151550293, 0.8045690655708313, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.8081142902374268, 0.0, 0.0, 0.79361492395401, 0.0, 1.4752510786056519, 0.0, 0.7008391618728638, 0.0, 0.0, 0.0, 1.0011858940124512, 1.8409404754638672, 0.8576440215110779, 0.0, 0.7103539705276489, 0.0, 0.0, 1.0023956298828125, 0.7796517014503479, 0.0, 0.3130819499492645, 0.0, 0.0, 0.9271455407142639, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.6693081259727478, 0.6591944098472595, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.6969431638717651, 0.0, 0.0, 0.0, 0.0, 0.0, 0.9635941982269287, 0.0, 0.8353727459907532, 0.0, 0.0, 0.0, 0.6496340036392212, 0.6984135508537292, 0.8035662770271301, 0.0, 0.0, 0.8317883014678955, 0.6715911626815796, 0.0, 0.8622066378593445, 0.0, 0.9849876165390015, 0.0, 0.8220551609992981, 0.0, 0.7016071677207947, 0.0, 0.0, 0.0, 0.0, 0.672482430934906, 0.0, 0.8951156139373779, 0.0, 0.0, 0.0, 0.0, 0.8804540634155273, 0.0, 0.8863659501075745, 1.9170818328857422, 0.0, 0.0, 0.0, 0.8489586710929871, 0.6527884006500244, 0.0, 0.7782770395278931, 0.0, 0.0, 0.0, 0.0, 0.9404365420341492, 0.0, 0.0, 0.0, 0.9119467735290527, 1.3186241388320923, 1.4247900247573853, 0.7155285477638245, 0.9291642308235168, 0.0, 0.6717998385429382, 0.0, 0.0, 0.0, 0.8739611506462097, 0.6972454786300659, 0.0, 1.0497007369995117, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.7123571634292603, 0.0, 0.8973782062530518, 0.0, 0.6393315196037292, 0.0, 0.0, 0.0, 0.0, 0.0, 0.682075023651123, 0.0, 0.8884515166282654, 0.0, 0.0, 0.8629441857337952, 0.0, 0.0, 3.5794994831085205, 5.259190559387207, 16.275251388549805, 15.828630447387695, 17.459815979003906, 11.2410249710083, 12.95916748046875, 0.8325950503349304, 17.264795303344727, 5.231194972991943, 11.788715362548828, 13.372735023498535, 9.874418258666992, 9.585014343261719, 10.622732162475586, 0.17843158543109894, 1.1537890434265137, 2.8726518154144287, 0.3883950710296631, 10.059682846069336, 5.796578884124756, 0.4386732280254364, 4.0493011474609375, 8.01463508605957, 1.1210452318191528, 6.7083563804626465, 5.886682033538818, 3.543473958969116, 17.824193954467773, 4.235814571380615, 3.74895977973938, 3.0164952278137207, 1.468520164489746, 7.490574836730957, 2.7813310623168945, 3.0881741046905518, 8.613974571228027, 6.40812349319458, 9.8677339553833, 10.004401206970215, 0.3919622600078583, 10.057321548461914, 9.142032623291016, 3.511949062347412, 7.296238899230957, 5.855912208557129, 5.715523719787598, 1.3154325485229492, 9.917375564575195, 2.1591315269470215, 9.6426362991333, 1.0009475946426392, 8.9176025390625, 3.13055157661438, 2.0951831340789795, 0.8531008958816528, 15.825373649597168, 6.730392932891846, 4.747975826263428, 11.519950866699219, 13.799840927124023, 10.095884323120117, 9.735567092895508, 19.559192657470703, 5.298473358154297, 11.685847282409668, 11.397789001464844, 6.387274265289307, 6.869878768920898, 3.3472392559051514, 2.139181137084961, 2.0623550415039062, 4.640389442443848, 4.172297954559326, 20.811153411865234, 9.4494047164917, 10.086273193359375, 1.5486942529678345, 8.268240928649902, 5.771872520446777, 10.514652252197266, 8.73259162902832, 2.4598398208618164, 4.111511707305908, 10.470922470092773, 4.022528648376465, 5.502430438995361, 9.94562816619873, 12.964680671691895, 12.802690505981445, 11.87685775756836, 19.83156967163086, 3.5171878337860107, 7.197744369506836, 4.059556007385254, 20.177562713623047, 0.6775469779968262, 4.476041793823242, 10.144206047058105, 7.86313533782959, 14.23621940612793, 27.504743576049805, 3.589337110519409, 15.45534610748291, 20.417741775512695, 3.6955437660217285, 2.5392346382141113, 14.747140884399414, 8.3154296875, 3.8206787109375, 4.037004470825195, 13.298784255981445, 3.6735546588897705, 1.921749234199524, 2.491082191467285, 6.536366939544678, 7.141772747039795, 10.334507942199707, 5.4254655838012695, 3.328312397003174, 5.417700290679932, 15.268346786499023, 4.899016380310059, 4.065462589263916, 10.34272289276123, 10.210506439208984, 5.130770206451416, 8.89155101776123, 1.756733775138855, 6.594151496887207, 4.339686870574951, 10.957969665527344, 14.501422882080078, 12.89188003540039, 0.47709617018699646, 5.800013065338135, 5.333886623382568, 1.9182677268981934, 2.487201452255249, 1.3408454656600952, 3.9111087322235107, 1.349609375, 2.4039595127105713, 17.88583755493164, 5.524857521057129, 35.784305572509766, 15.528326988220215, 1.5549553632736206, 3.3240199089050293, 18.84906768798828, 7.104069709777832, 5.08115291595459, 16.739120483398438, 6.504700660705566, 7.511229038238525, 0.7304150462150574, 0.24174536764621735, 12.282937049865723, 6.915319442749023, 0.04723227769136429, 19.295522689819336, 6.23649787902832, 5.050709247589111, 0.07290080934762955, 4.955596923828125, 10.250654220581055, 2.3044939041137695, 5.655325889587402, 8.661194801330566, 6.47348690032959, 19.021852493286133, 32.961029052734375, 5.985243797302246, 4.543829441070557, 5.78222131729126, 5.059074401855469, 0.6263728737831116, 22.26411247253418, 3.331113815307617, 13.548891067504883, 8.484724998474121, 8.486090660095215, 0.5322595834732056, 11.665563583374023, 33.43860626220703, 12.837885856628418, 15.590978622436523, 9.223156929016113, 3.9731228351593018, 5.821849346160889, 0.37589263916015625, 10.863398551940918, 11.183500289916992, 7.353213787078857, 6.942647457122803, 18.305822372436523, 16.932947158813477, 6.6716437339782715, 4.735979080200195, 10.304312705993652, 2.460603713989258, 8.757421493530273, 4.255965709686279, 3.463174343109131, 19.466060638427734, 2.3594701290130615, 3.283838987350464, 1.4308291673660278, 23.291406631469727, 10.659963607788086, 4.245340347290039, 10.130038261413574, 3.252803325653076, 5.148032188415527, 2.0914342403411865, 1.2820038795471191, 8.02988052368164, 10.979246139526367, 7.200527191162109, 2.15114426612854, 9.276591300964355, 11.213964462280273, 2.3345091342926025, 15.900187492370605, 10.994882583618164, 5.74565315246582, 12.633173942565918, 8.41689682006836, 2.750608444213867, 3.211332321166992, 16.343961715698242, 2.6772351264953613, 7.637927055358887, 6.476600170135498, 5.069215774536133, 6.55263090133667, 0.5276206135749817, 4.112788200378418, 2.986332893371582, 6.057596683502197, 4.102025985717773, 9.862314224243164, 7.907534122467041, 23.330942153930664, 6.836906433105469, 1.7914544343948364, 4.625866413116455, 5.498847484588623, 0.1318892389535904, 2.8394558429718018, 9.858765602111816, 11.393285751342773, 4.794058322906494, 2.150167465209961, 9.67081069946289, 10.395078659057617, 0.9968848824501038, 0.6548686027526855, 23.730093002319336, 1.5576269626617432, 4.372626304626465, 10.445714950561523, 3.393605947494507, 5.870281219482422, 13.815119743347168, 3.7774696350097656, 8.16089916229248, 7.538115501403809, 4.365720272064209, 4.667508125305176, 11.258978843688965, 21.276220321655273, 0.3004745841026306, 11.787948608398438, 11.09654712677002, 12.707402229309082, 1.1315717697143555, 10.667228698730469, 3.2918648719787598, 7.934054851531982, 22.334352493286133, 12.46993350982666, 13.717023849487305, 4.062182903289795, 8.831859588623047, 5.090256690979004, 11.127360343933105, 4.414024829864502, 6.609350204467773, 19.453876495361328, 10.357770919799805, 16.233823776245117, 14.72935962677002, 1.8531243801116943, 10.039104461669922, 12.844785690307617, 14.237333297729492, 4.626801490783691, 2.214808464050293, 10.245001792907715, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.189406156539917, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 2.6806399822235107, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.2530903816223145, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 2.029350519180298, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.1430530548095703, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 2.0191946029663086, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 1.072676420211792, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.7003874778747559, 9.5367431640625e-07, 9.5367431640625e-07, 1.6904407739639282, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 2.0762975215911865, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.15488284826278687, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.10872173309326172, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 2.319145679473877, 9.5367431640625e-07, 9.5367431640625e-07, 1.2434828281402588, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.828802466392517, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.584463119506836, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.1708941459655762, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 2.415869951248169, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.7238918542861938, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 5.9604643443123e-10, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 5.9604643443123e-10, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 5.9604643443123e-10, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.411880425669209e-14, 1.4218727039413785e-14, 5.5343586938467245e-15, 1.2571953535449234e-14, 1.4356491866087014e-14, 1.0346082240171757e-14, 1.3521184395921555e-14, 1.174103115485171e-14, 1.3780178272071713e-14, 1.2946234524951333e-14, 5.614536291534975e-15, 1.0252732433120755e-14, 7.610110763398795e-15, 4.8189262909920094e-15, 4.9937657497665586e-15, 7.106802939107343e-15, 8.83331443066052e-15, 4.192507310014828e-15, 7.243116798341925e-15, 9.006717321556525e-15, 4.3294234096749075e-15, 5.36735810148254e-15, 1.0529707971708175e-14, 9.606894374794821e-15, 4.188002365284856e-15, 1.4760377504128598e-14, 1.456539899000013e-14, 1.2939796227519253e-14, 1.0745434557879636e-14, 7.1389148051707e-15, 1.2633152512921304e-14, 8.662771122994444e-15, 4.0134504741958996e-15, 4.320810355150752e-15, 7.301769594774549e-15, 1.005429209533686e-14, 8.819128322859904e-15, 8.144781676628233e-15, 4.154541175736522e-15, 1.2262419744435253e-14, 9.09446400566144e-15, 8.952607162820026e-15, 7.766408670957948e-15, 1.384260629435025e-14, 1.3095016709169498e-14, 1.5085599192358676e-14, 1.4184796593612672e-14, 1.0412383744118087e-14, 6.486582545238168e-15, 1.2022034335103324e-14, 5.913392385215868e-15, 1.1002047424415063e-14, 1.106091536721629e-14, 5.8980945466719815e-15, 1.018101500050968e-14, 1.3115897765385211e-14, 7.408311092946089e-15, 9.775191351084778e-15, 1.2743063508157022e-14, 1.3779934326582904e-14, 1.5136875178853662e-14, 1.3470914684567906e-14, 1.1017059389339251e-14, 1.1220268522616188e-14, 8.489047206611429e-15, 9.158133778240651e-15, 9.12669869150215e-15, 1.2502795836404762e-14, 1.0798236897745575e-14, 1.5004082435580816e-14, 1.2948763765331835e-14, 1.1415928898267196e-14, 4.283940281506193e-15, 7.593739310594264e-15, 1.3996200472741766e-14, 1.4816518847872613e-14, 4.203949031066339e-15, 4.176453918081991e-15, 1.1102036275706644e-14, 5.937819544865261e-15, 1.0650091682303745e-14, 1.3296163317219872e-14, 6.6341695659677576e-15, 7.922134831277704e-15, 1.2463118272056529e-14, 8.901666601372153e-15, 1.3537842145862258e-14, 1.2293926828974271e-14, 5.517032211394164e-15, 4.480899158665341e-15, 1.0759305569423873e-14, 8.032866601439311e-15, 1.098830516187881e-14, 1.3315730625334393e-14, 6.1302069852080775e-15, 5.834238850360848e-15, 6.971508907541255e-15, 1.183764881501322e-14, 1.0255403128003448e-14, 5.063618015827779e-15, 7.871091778843212e-15, 7.538616100452849e-15, 1.2269414542513679e-14, 9.082845254723953e-15, 7.676127664274848e-15, 1.2555210235180858e-14, 1.3139517279119398e-14, 1.1673819937520029e-14, 6.2414503632698265e-15, 9.397090242990562e-15, 1.4978723963205917e-14, 5.1366233620351535e-15, 1.2256094102385158e-14, 1.3039690211120742e-14, 1.3797062179809333e-14, 1.0588408201985845e-14, 1.0638781251359058e-14, 1.0091382821064178e-14, 8.389351428719598e-15, 1.4424569598123736e-14, 5.5709331529926916e-15, 1.1642946433625557e-14, 9.833622224885222e-15, 1.3250899570584496e-14, 6.788918250266382e-15, 8.768713768872276e-15, 1.1454340148359284e-14, 6.4390089397556305e-15, 1.468277234550116e-14, 1.3203426762022682e-14, 7.74058094233027e-15, 6.127584571203378e-15, 1.4519049347126375e-14, 8.3328035091609e-15, 1.1884433832821863e-14, 1.498678432873199e-14, 1.333958730829381e-14, 8.415497641735444e-15, 1.3509054884116873e-14, 9.364846239787433e-15, 6.2433519522364124e-15, 6.412678497073757e-15, 5.7455240075972216e-15, 1.3199918351555154e-14, 1.0971544920951488e-14, 4.2059226178334415e-15, 7.196564714593776e-15, 8.90540625183428e-15, 4.355475178517134e-15, 6.5311513013403214e-15, 1.0907126371246904e-14, 5.596371246464633e-15, 6.0405053490609e-15, 1.0440347689838741e-14, 5.966074022886823e-15, 1.4402228257106957e-14, 3.994354963432999e-15, 6.03951050886435e-15, 8.52751944307572e-15, 1.0659285377913243e-14, 4.449741051700592e-15, 1.0546924763394066e-14, 6.845311586312205e-15, 1.2460500940249513e-14, 5.85511863602714e-15, 8.72838314212171e-15, 1.2932148367038494e-14, 6.63731544633386e-15, 7.458905217918536e-15, 1.174195696186306e-14, 1.0293462859422425e-14, 6.1318290533020695e-15, 9.528326139706354e-15, 9.618524137160623e-15, 6.2885102432698545e-15, 1.0096766562476926e-14, 1.1228866754063767e-14, 1.2369180624140132e-14, 1.2888774350908443e-14, 1.0640266947148543e-14, 1.0010700391739364e-14, 4.173064092227079e-15, 9.399079923383662e-15, 1.1787922898811708e-14, 1.2931383496287124e-14, 1.1923035665327084e-14, 1.0362444375613868e-14, 4.521260278602009e-15, 6.63572048329418e-15, 5.819269660600496e-15, 4.1223950048388004e-15, 1.1907517174700438e-14, 5.344546657180035e-15, 5.018197144580688e-15, 1.0274984835678073e-14, 9.514920996283108e-15, 1.1628185190453756e-14, 6.809721802967421e-15, 9.390341931499787e-15, 6.580998766769763e-15, 1.3869044733732898e-14, 6.325881336902714e-15, 6.536593064509957e-15, 8.000596340214817e-15, 1.1872950607155937e-14, 1.3127461459181127e-14, 4.108179674401505e-15, 9.662092970868542e-15, 1.0229323830590435e-14, 1.1726736626833847e-14, 5.194261412996967e-15, 1.4555207489578767e-14, 1.443997204523661e-14, 9.556088491585561e-15, 4.938873779619744e-15, 1.3690658748008195e-14, 1.3850905523167447e-14, 6.098329747271109e-15, 1.3833454103355167e-14, 1.430133138649592e-14, 1.0586940293888254e-14, 9.830869367806645e-15, 8.061015200342466e-15, 1.0514677372059147e-14, 6.998445825813363e-15, 1.2244841269680885e-14, 1.4460309306300184e-14, 1.3031144495715893e-14, 8.203019426916702e-15, 5.348055491164036e-15, 1.1985471310902145e-14, 4.867614591833134e-15, 5.9309878006291814e-15, 6.317804030717697e-15, 7.571622433308507e-15, 6.5942908312945515e-15, 7.194282807833872e-15, 1.2806329246020393e-14, 1.3974819667087173e-14, 1.141971259444258e-14, 7.220056326352926e-15, 1.3250902111683338e-14, 1.2331527468535837e-14, 1.326062859101666e-14, 5.458864764840317e-15, 7.441604569970867e-15, 6.613444363814339e-15, 1.4043273481752477e-14, 1.3044595378918292e-14, 7.805295106533446e-15, 9.961256537509289e-15, 1.4742278104111668e-14, 9.366589433592882e-15, 1.1268178400178786e-14, 8.671750519268287e-15, 1.4888030451477505e-14, 7.714998006224348e-15, 8.336242462926753e-15, 1.4917676604631405e-14, 1.0990000074806265e-14, 1.3374973803731253e-14, 9.95854433801218e-15, 9.604524376608404e-15, 1.0281490048712986e-14, 9.78770033364983e-15, 5.179980013989786e-15, 4.195520629724685e-15, 1.0338507224524462e-14, 6.708325606433977e-15, 5.741745817135994e-15, 1.0696402361661927e-14, 6.4151166814124284e-15, 1.1014630945879473e-14, 7.536730605112261e-15, 1.4575549832840026e-14, 1.4710565190566467e-14, 1.3403435804824892e-14, 1.2018902007264378e-14, 6.178684798361809e-15, 7.339122900715516e-15, 6.309280761685951e-15, 8.733200218492745e-15, 9.738126036345877e-15, 1.2301974489006134e-14, 1.4026815631587326e-14, 9.618890055393837e-15, 7.676933192607687e-15, 6.396879215025096e-15, 5.01821493227258e-15, 1.4480716024065435e-14, 5.010696667832751e-15, 6.6005664984007586e-15, 1.2927933531092957e-14, 4.690117567186574e-15, 1.3486849068371654e-14, 6.883503878387428e-15, 1.1020738900462124e-14, 8.934904174222411e-15, 6.129644131814627e-15, 9.252858319765047e-15, 0.0, 2.0338497161865234, 0.682262122631073, 0.0, 0.8124330639839172, 0.0, 0.0, 0.0, 0.0, 0.8539921641349792, 0.0, 3.756335973739624, 0.0, 0.0, 2.1324501037597656, 0.9599154591560364, 0.0, 1.5610661506652832, 0.8118235468864441, 1.4286963939666748, 0.7485016584396362, 0.0, 2.1203994750976562, 1.377166748046875, 0.0, 8.02337646484375, 0.8513209223747253, 2.476360321044922, 1.4817578792572021, 2.071949005126953, 0.0, 0.6598731875419617, 0.0, 0.8084263205528259, 0.0, 0.0, 0.0, 0.0, 1.526953101158142, 1.3209844827651978, 1.3761813640594482, 0.9983396530151367, 0.7289429903030396, 0.9662753343582153, 0.0, 0.8178964257240295, 2.410032272338867, 0.7828167676925659, 0.0, 0.0, 0.6534299850463867, 0.0, 0.813950777053833, 1.405853509902954, 1.939333200454712, 0.0, 0.0, 0.0, 1.1885147094726562, 0.0, 0.0, 1.0190238952636719, 0.6527688503265381, 2.1018028259277344, 0.8009910583496094, 0.0, 0.9534953832626343, 0.0, 1.5560150146484375, 0.8037486672401428, 2.5120697021484375, 0.0, 0.0, 0.7938992977142334, 4.123176574707031, 0.0, 0.0, 0.0, 0.0, 0.7825179696083069, 0.0, 0.9128136038780212, 0.8821063041687012, 0.0, 1.4712344408035278, 0.0, 1.6667535305023193, 0.9523931741714478, 2.7788162231445312, 0.0, 0.0, 0.0, 0.0, 1.7914248704910278, 1.419593334197998, 1.4178560972213745, 0.0, 1.358972430229187, 0.0, 2.193413257598877, 0.0, 1.509065866470337, 0.0, 2.3274307250976562, 3.9653966426849365, 2.3889710903167725, 1.001487135887146, 0.0, 0.0, 0.7164860367774963, 2.2248003482818604, 2.6803929805755615, 1.5491536855697632, 2.710468053817749, 1.0131759643554688, 1.9358776807785034, 0.7801719307899475, 1.329628586769104, 0.0, 0.0, 0.0, 1.3416558504104614, 2.228853464126587, 0.0, 0.0, 1.7211723327636719, 0.6655920147895813, 0.9302859306335449, 0.7665835618972778, 2.296100616455078, 1.803094744682312, 1.895424723625183, 0.0, 0.0, 2.331983804702759, 1.570154070854187, 1.3480225801467896, 0.9392322301864624, 0.0, 1.7640800476074219, 2.5366568565368652, 0.0, 0.0, 0.8715651035308838, 4.0844879150390625, 0.7728189826011658, 2.042257308959961, 0.0, 0.0, 0.0, 1.0035686492919922, 2.6846039295196533, 1.704356074333191, 0.9165483117103577, 0.0, 0.0, 1.36646568775177, 4.376895427703857, 0.8416197299957275, 1.3117355108261108, 0.0, 0.9348690509796143, 4.343013763427734, 1.567744255065918, 0.904271125793457, 0.0, 9.123969078063965, 0.0, 0.0, 1.0427474975585938, 0.8360617160797119, 0.0, 1.0151252746582031, 0.0, 0.0, 0.0, 3.05242919921875, 0.0, 1.333522915840149, 2.4273529052734375, 0.0, 3.030687093734741, 0.8635965585708618, 0.8276827931404114, 2.0292510986328125, 0.0, 1.9857909679412842, 1.9497184753417969, 0.6587580442428589, 0.8554041981697083, 1.5776406526565552, 0.0, 1.1364402770996094, 0.8365026712417603, 2.6981585025787354, 0.0, 0.9338709712028503, 0.0, 2.0209767818450928, 1.2252979278564453, 4.250796794891357, 0.7384951114654541, 0.0, 3.7514724731445312, 1.676194667816162, 0.0, 12.379487991333008, 0.878624677658081, 0.0, 1.0365104675292969, 1.2843035459518433, 0.7542940378189087, 0.0, 1.0028152465820312, 1.3437695503234863, 0.8442286252975464, 1.7254317998886108, 1.7992714643478394, 0.6440553069114685, 0.0, 0.0, 2.2212066650390625, 0.0, 0.0, 0.0, 1.4818671941757202, 0.0, 1.2914596796035767, 0.0, 0.0, 0.8640419840812683, 0.9138778448104858, 1.9505889415740967, 1.2160072326660156, 1.6939542293548584, 0.0, 1.555719256401062, 1.6754915714263916, 2.238511323928833, 1.3462295532226562, 1.6389864683151245, 0.8385137915611267, 0.0, 2.6018600463867188, 0.0, 1.4479459524154663, 2.0138015747070312, 0.0, 2.7330780029296875, 3.0462310314178467, 0.0, 0.0, 0.0, 1.321821928024292, 0.0, 0.8849882483482361, 1.186441421508789, 1.069732666015625, 2.626587390899658, 1.4308607578277588, 1.4185744524002075, 0.0, 1.2987359762191772, 0.0, 1.9109388589859009, 0.0, 0.0, 0.6396368741989136, 0.9123737812042236, 0.0, 2.2856438159942627, 0.0, 0.0, 0.6894392371177673, 0.9292450547218323, 2.2036213874816895, 2.540548324584961, 1.5294303894042969, 1.440063714981079, 0.0, 0.0, 1.6389126777648926, 2.0537126064300537, 0.0, 0.0, 1.780013084411621, 1.4361764192581177, 2.00643253326416, 0.0, 0.0, 1.907348590179936e-08, 0.0, 0.0, 0.8487640023231506, 0.0, 0.0, 0.0, 0.8598136901855469, 1.5618188381195068, 0.7935613989830017, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.840012788772583, 9.5367431640625e-07, 1.8693796396255493, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.878477931022644, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.0575790405273438, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.9175516963005066, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.2426344156265259, 9.5367431640625e-07, 2.045156478881836, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.513573169708252, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 1.4444499015808105, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.2916234731674194, 9.5367431640625e-07, 1.4912948608398438, 9.5367431640625e-07, 1.8318891525268555, 1.7296279668807983, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.4216774702072144, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.231934666633606, 0.0, 0.0, 1.005984902381897, 9.5367431640625e-07, 2.7115912437438965, 9.5367431640625e-07, 9.5367431640625e-07, 1.5894924402236938, 2.2459912300109863, 1.6827013492584229, 2.8625307083129883, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 2.267425537109375, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.153793454170227, 9.5367431640625e-07, 1.7740846872329712, 9.5367431640625e-07, 9.5367431640625e-07, 1.53740394115448, 1.3057421445846558, 9.5367431640625e-07, 1.080073356628418, 1.575342059135437, 2.3328306674957275, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.3150484561920166, 1.5489232540130615, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.8762875199317932, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 2.301119565963745, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.8885065913200378, 1.5901092290878296, 1.2419686317443848, 9.5367431640625e-07, 9.5367431640625e-07, 1.8694788217544556, 9.5367431640625e-07, 1.053039789199829, 9.5367431640625e-07, 9.5367431640625e-07, 1.267136573791504, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.0624847412109375, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.5633095502853394, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.1779495477676392, 1.4742249250411987, 0.0, 0.0, 9.5367431640625e-07, 2.2285895347595215, 1.2665833234786987, 9.5367431640625e-07, 1.4643014669418335, 2.6987645626068115, 9.5367431640625e-07, 1.7931442260742188, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.5756746530532837, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.958052158355713, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 1.8239601850509644, 1.127530813217163, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.5469993352890015, 2.587341785430908, 1.4382389783859253, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.8927379846572876, 0.5935907959938049, 1.1511945724487305, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.821216106414795, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.2973313331604004, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.8230915069580078, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.6893879175186157, 9.5367431640625e-07, 0.0, 2.1335644721984863, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.2516833543777466, 9.5367431640625e-07, 1.2148516178131104, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.0567277669906616, 8.201598689083767e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.003558338852599263, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 5.9604643443123e-10, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 5.9604643443123e-10, 0.0, 0.0, 0.0, 0.0, 0.0, 5.9604643443123e-10, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0003598368202801794, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.38418573772492e-09, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.007379239425063133, 1.3651391147606433e-14, 1.3326077979818052e-14, 1.0623830272807073e-14, 1.37180052067103e-14, 1.3779272793851098e-14, 7.897596286795747e-15, 1.2298768469300777e-14, 5.75287640458555e-06, 7.963492061960342e-15, 6.3929633817099395e-15, 1.2041155256854643e-14, 6.81702280345628e-15, 9.879436542936312e-15, 1.1721519750911708e-14, 1.3011347641672666e-14, 3.9187094155290324e-15, 5.760088315608786e-15, 1.3610421858013637e-14, 4.496362592150416e-15, 6.666297525657113e-15, 5.85496913471195e-15, 5.5912043454863815e-15, 1.173658592594452e-14, 0.11510471254587173, 1.5206204825586427e-14, 8.51163503421586e-15, 4.971365116443471e-15, 1.1566029912784236e-14, 4.944128772024509e-15, 1.2991031556432771e-14, 4.957628359621375e-15, 6.519492739854313e-15, 1.3709760188001727e-14, 1.1879024680420697e-14, 1.1130807443826031e-14, 1.3697660322350199e-14, 1.186313349529726e-14, 6.210182142021934e-15, 1.3319048453388788e-14, 1.0014811889665336e-14, 6.780316207170541e-15, 8.791953811846092e-15, 6.407426469284307e-15, 5.6925543787242e-15, 3.925661861960096e-15, 1.2576055716012786e-14, 7.05023680834028e-15, 6.10539400205121e-15, 6.66574949534024e-15, 0.10446321219205856, 1.3236680428498938e-14, 0.10794337838888168, 4.220586452216308e-15, 1.238171247659476e-14, 4.9400791075036865e-15, 8.417981142336793e-15, 1.4074392625201652e-14, 7.047280239837889e-15, 5.014391002032201e-15, 6.925255402907013e-15, 1.2911345237853929e-14, 1.0716828561184964e-14, 1.0791827399433702e-14, 1.0261442472917371e-14, 1.2908148535510991e-14, 5.209209850450111e-15, 8.759770795015165e-15, 6.2899120827975604e-15, 1.1559089324814434e-14, 1.4528600490639615e-14, 4.447531566257679e-15, 9.78993988876237e-15, 1.376019507078009e-14, 5.747300235687614e-15, 7.233291216153775e-15, 4.388440430274851e-15, 7.904119287522552e-15, 7.755863957797579e-15, 4.852901629539327e-15, 1.0803292837407736e-14, 7.963226940647852e-15, 1.0214083166770489e-14, 1.1085630941584223e-14, 1.3243416881528452e-14, 1.2773351712284942e-14, 1.1543442085179805e-14, 1.5157439444747102e-14, 1.148992315544049e-14, 1.4029399929109398e-14, 8.514696211287236e-15, 5.3950645491872284e-15, 4.538547374022522e-15, 9.727409375497216e-15, 1.1615016369222794e-14, 1.4153885820268521e-14, 1.5249515314245433e-14, 7.23469305568148e-15, 0.0013931868597865105, 6.531594723088209e-15, 5.148197220226436e-15, 5.572739450752711e-15, 8.874830056504295e-15, 8.289851315438582e-15, 0.007727086544036865, 8.352233597937967e-15, 9.832050131735118e-15, 1.398301132272007e-14, 9.504886196956986e-15, 1.4775596992124863e-14, 1.455493813310154e-14, 6.348370061652316e-15, 1.2804498807821377e-14, 7.684230381448283e-15, 6.709888382221661e-15, 1.187399838691169e-14, 5.4750583407259246e-15, 7.033973775752997e-15, 1.0697738132619747e-14, 5.7392220824696496e-15, 8.701981125155793e-15, 6.827852119686926e-15, 1.4824242094285678e-14, 6.128854697107786e-15, 7.518765883333944e-15, 4.74986811831884e-15, 3.984965603212685e-15, 4.910609137202815e-15, 0.0029605429153889418, 1.139451167019587e-14, 8.303769760827865e-15, 5.18763083908586e-15, 7.138387103644561e-15, 8.776741947146352e-15, 1.3314399936574257e-14, 0.011262724176049232, 1.2350398515567716e-14, 1.1290137729336354e-14, 0.0001821913756430149, 7.761053728665406e-15, 4.837456830779092e-15, 4.8434195192112884e-15, 1.2003518194876345e-14, 7.204217657272218e-15, 8.659584585046873e-15, 1.1272655816337972e-14, 1.324065640115335e-14, 1.1840649852745341e-14, 1.275399108020955e-14, 3.3454711228841916e-05, 1.2853787655022104e-14, 9.758509037188605e-15, 6.507423367388887e-15, 1.1975142591143326e-14, 1.428779749406469e-14, 9.628641098682628e-15, 7.077467223528611e-15, 1.4076073138569005e-14, 5.072927754951051e-15, 5.961788036173716e-15, 1.3840270177481722e-14, 5.497000729224547e-15, 3.853146524312708e-15, 1.2147069103612268e-14, 1.3127591902255004e-14, 1.0878082458518502e-14, 5.954912669740853e-15, 1.3197202763926257e-14, 7.941377725773427e-15, 6.085262993510291e-15, 3.919107257388532e-05, 8.90853434450849e-15, 1.1384790273060233e-14, 7.604107840901604e-15, 1.218649086401043e-14, 1.1550023531179971e-14, 1.1344538420373761e-14, 1.098596650391144e-14, 4.319220050792282e-15, 1.1753634158073907e-14, 1.2268031337710813e-14, 1.18694760780063e-14, 9.615028432187304e-15, 8.182419585639478e-15, 4.316869957880125e-15, 1.1458991206272657e-14, 1.2779464749065276e-14, 1.2247787250271435e-14, 9.909490118937842e-15, 1.2454580179948205e-14, 1.3297355939609606e-14, 4.647976831027726e-15, 6.351167387960623e-15, 1.4929489326113814e-14, 3.8534103750757775e-15, 1.2965197051541515e-14, 1.2557362545899831e-14, 1.4729599714957166e-14, 1.1801834567937413e-14, 1.1786188175335732e-14, 1.2590030912609535e-14, 7.949898877222805e-15, 1.2713296229291664e-14, 1.4863535952708805e-14, 1.2371614149797594e-14, 5.348090643031347e-15, 8.185150419861426e-15, 6.108823214938169e-15, 1.32579782249247e-14, 3.969176485559391e-15, 5.0021670460539e-15, 1.0509069166915377e-14, 7.863176255951121e-15, 8.029919773815813e-15, 1.2445720215319925e-14, 1.1159709902052242e-14, 1.3360218489790084e-14, 1.1892094398796831e-14, 7.137019992467693e-15, 9.924645232430116e-15, 6.021552563349611e-15, 1.2859871045649285e-14, 1.3638868612514225e-14, 5.260371911013691e-15, 6.342974461778306e-15, 6.319079238819789e-15, 3.9919447311815865e-15, 7.646722915510915e-15, 1.2003113313127558e-14, 1.1031475043068572e-14, 6.930174546748193e-15, 1.2231028703410009e-14, 1.483530434457682e-14, 1.4805554853403353e-14, 6.991390888395682e-15, 6.156512863934481e-15, 8.399298983652152e-15, 9.715919373567711e-15, 7.580099539044628e-15, 1.4230690532760805e-14, 7.735341196518555e-15, 0.0011826591799035668, 6.614905072131879e-15, 5.013876429516744e-15, 1.064917095749008e-14, 1.2706514883515947e-14, 7.323190210977663e-15, 9.576490974186076e-15, 6.392370035130388e-15, 1.0897604873886819e-14, 4.545918254729529e-15, 7.152080238269874e-15, 7.466777542130317e-15, 6.22360592017002e-15, 9.993309958299286e-15, 1.1957464166501182e-14, 1.3972477620988015e-14, 4.619200580710655e-15, 1.5076918798715214e-14, 0.001723944558762014, 1.011453477261148e-14, 1.4267329789927237e-14, 1.5011378777388465e-14, 8.377213446585444e-15, 1.5168637220309804e-14, 1.0816617512700993e-14, 1.0311364900762645e-14, 9.93872969627706e-15, 9.885282764338262e-15, 3.921005298332565e-15, 6.88887406727302e-15, 1.4987695736183235e-14, 9.545962212701136e-15, 1.516244371539948e-14, 3.967227462747759e-15, 7.952495880239087e-15, 5.093618652270105e-15, 8.125221991810237e-15, 1.0171474021391808e-14, 6.5258204994867765e-15, 4.804466591549431e-15, 0.00018097893917001784, 5.606357341396287e-15, 6.6243634655373945e-15, 1.4183460822654852e-14, 1.1913079640065057e-14, 1.4303411699414376e-14, 8.032501530239045e-15, 7.846515964911576e-15, 1.0697223983620763e-14, 6.640773034824552e-15, 1.467760205639112e-14, 6.312090369971993e-15, 4.639310413427893e-15, 7.88344151921418e-15, 1.1626403033132733e-14, 1.4742445816635225e-14, 1.5083647628448202e-14, 4.9105163870950905e-15, 1.2836248990816257e-14, 8.727674175544858e-15, 0.0, 2.1039798259735107, 0.9297429323196411, 0.0, 0.0, 0.0, 2.0419273376464844, 3.1348016262054443, 7.629394360719743e-08, 2.0570356845855713, 0.0, 3.296215057373047, 4.21467399597168, 0.865577220916748, 6.863574504852295, 2.3748795986175537, 3.100576400756836, 0.7986164093017578, 1.9908639192581177, 2.584430456161499, 1.952425479888916, 0.0, 2.6354620456695557, 2.798696756362915, 2.499004364013672, 1.4447927474975586, 0.0, 3.8209457397460938, 0.8366644978523254, 0.0, 3.3255996704101562, 0.0, 2.365009069442749, 1.4535948038101196, 0.0, 1.2773479223251343, 0.0, 10.395530700683594, 1.7136999368667603, 1.698761224746704, 1.6458511352539062, 3.4616622924804688, 0.0, 1.6339950561523438, 22.315631866455078, 4.285541534423828, 7.512542724609375, 4.779518127441406, 2.4897117614746094, 0.0, 4.015970230102539, 0.0, 2.942765474319458, 2.543776512145996, 3.2135636806488037, 8.238727569580078, 0.0, 1.3056429624557495, 5.428794860839844, 3.58309268951416, 4.324664115905762, 0.0, 2.173238754272461, 0.0, 3.17031192779541, 10.891136169433594, 0.875807523727417, 0.8848364353179932, 3.61722731590271, 2.0974631309509277, 1.7805508375167847, 3.8785972595214844, 1.3379693031311035, 9.283671379089355, 0.0, 3.2837142944335938, 0.8111557364463806, 5.50123929977417, 1.0285720825195312, 2.0065765380859375, 1.2885262966156006, 0.0, 0.0, 0.7487130761146545, 0.0, 1.4105263948440552, 3.3263702392578125, 2.6719884872436523, 2.375230073928833, 0.8415035605430603, 1.7235440015792847, 0.8414466381072998, 2.041271209716797, 0.0, 2.7926952838897705, 1.2842930555343628, 0.0, 2.1421008110046387, 1.565240740776062, 0.0, 1.574689507484436, 0.6898483037948608, 1.0244102478027344, 1.6277800798416138, 0.0, 4.1004486083984375, 0.0, 2.623779296875, 7.011966228485107, 0.0, 1.2756048440933228, 3.010406970977783, 0.6896264553070068, 1.3232282400131226, 0.0, 5.079799652099609, 0.7687395811080933, 1.343017339706421, 2.9349827766418457, 2.318828582763672, 6.526099681854248, 0.0, 1.8341102600097656, 1.5326910018920898, 2.8851585388183594, 1.4097956418991089, 2.2066807746887207, 1.4598671197891235, 0.0, 1.379750370979309, 8.012569427490234, 1.8333125114440918, 13.509288787841797, 2.9833824634552, 5.413012981414795, 2.151320695877075, 1.3665580749511719, 0.0, 2.7493481636047363, 0.0, 1.3276293277740479, 6.175457000732422, 0.6450541615486145, 4.818632125854492, 1.3879318237304688, 0.0, 2.606395721435547, 1.6324278116226196, 0.0, 2.2105724811553955, 1.4576168060302734, 6.587007999420166, 2.2370262145996094, 0.0, 0.0, 0.0, 3.634814977645874, 0.0, 3.40104603767395, 1.629178762435913, 1.3045814037322998, 4.264568328857422, 0.0, 0.0, 1.5597635507583618, 2.4890670776367188, 1.8048269748687744, 0.0, 1.4717597961425781, 5.042985916137695, 2.2788987159729004, 3.0414464473724365, 2.100059986114502, 0.0, 4.576444625854492, 0.0, 1.3248380422592163, 1.6811230182647705, 3.604058265686035, 12.879413604736328, 5.49848747253418, 0.0, 0.0, 1.85433828830719, 2.3519058227539062, 5.7409515380859375, 2.573779821395874, 2.917766571044922, 3.3884639739990234, 2.344404458999634, 2.0144805908203125, 1.0065422058105469, 1.9622231721878052, 1.7394338846206665, 1.3031902313232422, 2.8295397758483887, 2.0768661499023438, 0.7919225692749023, 3.1754417419433594, 0.6514674425125122, 2.005505323410034, 0.0, 10.82162857055664, 2.485149383544922, 0.0, 0.0, 1.3847854137420654, 1.2947726249694824, 0.0, 3.129497528076172, 2.84956955909729, 0.0, 0.0, 2.1605217456817627, 4.006689071655273, 1.4840126037597656, 5.109485149383545, 1.6177266836166382, 4.220606803894043, 3.1239750385284424, 4.637359619140625, 0.0, 5.098577499389648, 0.0, 2.0763189792633057, 0.733941912651062, 1.5670340061187744, 3.3864102363586426, 1.024566650390625, 4.93785285949707, 1.556660771369934, 4.15324592590332, 0.0, 0.0, 3.9218597412109375, 0.0, 1.4320939779281616, 2.0712902545928955, 4.441535949707031, 1.6983528137207031, 5.568084716796875, 0.0, 2.928048849105835, 1.2262496948242188, 1.3654714822769165, 1.5690523386001587, 6.6144561767578125, 2.7221641540527344, 0.7489641904830933, 5.091760635375977, 18.56947135925293, 1.7832319736480713, 0.0, 1.3247172832489014, 2.075042486190796, 0.906408429145813, 0.7084430456161499, 0.0, 2.78995418548584, 4.503206253051758, 0.0, 1.0576229095458984, 0.0, 0.0, 1.795308232307434, 2.283015251159668, 3.832275390625, 0.0, 1.6301946640014648, 2.5194530487060547, 1.2771857976913452, 2.189067840576172, 1.6324386596679688, 2.6498162746429443, 2.1399171352386475, 2.7219738960266113, 5.111549377441406, 0.0, 1.3722528219223022, 2.044994354248047, 0.0, 2.3269786834716797, 1.9652671813964844, 2.9833667278289795, 5.975028991699219, 0.0, 5.099937438964844, 1.2059173583984375, 0.0, 0.0, 3.6080589294433594, 1.3854299783706665, 2.43996524810791, 0.0, 0.8637551665306091, 2.1020126342773438, 1.9063148498535156, 0.0, 0.8821536302566528, 5.982311248779297, 9.5367431640625e-07, 1.8977738618850708, 1.4633963108062744, 9.5367431640625e-07, 9.5367431640625e-07, 2.4782423973083496, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.8062124252319336, 1.720778465270996, 1.587817668914795, 0.7946235537528992, 9.5367431640625e-07, 2.2065212726593018, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.2827956676483154, 9.5367431640625e-07, 1.367640495300293, 9.5367431640625e-07, 9.5367431640625e-07, 1.2023780345916748, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.485039472579956, 2.241605520248413, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.8997073769569397, 1.507735252380371, 9.5367431640625e-07, 9.5367431640625e-07, 1.4296883344650269, 1.7418705224990845, 9.5367431640625e-07, 2.291283130645752, 9.5367431640625e-07, 0.0, 1.0098963975906372, 9.5367431640625e-07, 9.5367431640625e-07, 1.1129069328308105, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.32103824615478516, 2.0099565982818604, 9.5367431640625e-07, 9.5367431640625e-07, 1.0773205757141113, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.1417090892791748, 1.6814202070236206, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.6228219270706177, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.9707131385803223, 1.5544041395187378, 1.0082978010177612, 9.5367431640625e-07, 0.9758307933807373, 9.5367431640625e-07, 1.2573670148849487, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.399981141090393, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.4918452501296997, 1.5069537162780762, 0.0, 1.9324984550476074, 9.5367431640625e-07, 0.8998267650604248, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.3089094161987305, 9.5367431640625e-07, 1.5366462469100952, 1.4675582647323608, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.234608769416809, 9.5367431640625e-07, 0.8592660427093506, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 1.1913803815841675, 9.5367431640625e-07, 2.3693690299987793, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.3747183084487915, 0.0, 1.9118579626083374, 9.5367431640625e-07, 1.7957711219787598, 1.7030245065689087, 9.5367431640625e-07, 9.5367431640625e-07, 1.2780972719192505, 0.935786247253418, 9.5367431640625e-07, 1.021028995513916, 1.5198266506195068, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.9276162385940552, 1.8586732149124146, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.1048706769943237, 9.5367431640625e-07, 0.38767528533935547, 9.5367431640625e-07, 9.5367431640625e-07, 1.5283703804016113, 1.5840396881103516, 9.5367431640625e-07, 1.3337430953979492, 9.5367431640625e-07, 9.5367431640625e-07, 1.8305803537368774, 1.2793129682540894, 1.3655331134796143, 9.5367431640625e-07, 0.8712837100028992, 1.7221884727478027, 9.5367431640625e-07, 9.5367431640625e-07, 1.8375910520553589, 9.5367431640625e-07, 1.0625828504562378, 1.533913254737854, 1.674702525138855, 9.5367431640625e-07, 0.9748907089233398, 1.2638912200927734, 9.5367431640625e-07, 9.5367431640625e-07, 2.305576801300049, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.9169257879257202, 1.427608609199524, 1.6672886610031128, 0.8127480745315552, 1.4341808557510376, 2.1733336448669434, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.0415104627609253, 9.5367431640625e-07, 1.7527364492416382, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 2.4084811210632324, 9.5367431640625e-07, 0.7480632066726685, 1.7874139547348022, 9.5367431640625e-07, 9.5367431640625e-07, 1.1169581413269043, 9.5367431640625e-07, 9.5367431640625e-07, 1.4078023433685303, 9.5367431640625e-07, 1.036019206047058, 1.3672966957092285, 9.5367431640625e-07, 9.5367431640625e-07, 1.1729800701141357, 1.4132025241851807, 1.6179085969924927, 1.635550618171692, 1.954577922821045, 1.5447180271148682, 1.268361210823059, 9.5367431640625e-07, 1.301000952720642, 1.2474925518035889, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.8791565895080566, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.9934157133102417, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.4297170639038086, 9.5367431640625e-07, 9.5367431640625e-07, 1.581270456314087, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.851833462715149, 9.5367431640625e-07, 9.5367431640625e-07, 1.2590874433517456, 9.5367431640625e-07, 1.3632363080978394, 2.895206928253174, 2.031275749206543, 9.5367431640625e-07, 9.5367431640625e-07, 1.244343638420105, 9.5367431640625e-07, 1.3391790390014648, 9.5367431640625e-07, 1.0601122379302979, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.9604590535163879, 1.9377799034118652, 9.5367431640625e-07, 9.5367431640625e-07, 1.4857224225997925, 9.5367431640625e-07, 2.3834218978881836, 1.439426064491272, 1.5656232833862305, 9.5367431640625e-07, 0.9251238703727722, 0.0, 1.3208893537521362, 1.1065425872802734, 1.1518936157226562, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.8794965744018555, 9.5367431640625e-07, 1.5875377655029297, 9.5367431640625e-07, 0.0, 0.0, 0.0, 2.1457671550706436e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.00016927719116210938, 0.0, 1.6810894521768205e-05, 0.0, 0.0, 0.02756969816982746, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 5.9604643443123e-10, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.19209286886246e-09, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.2400149898894597e-05, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.19209286886246e-09, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.039227504283189774, 0.0, 5.9604643443123e-10, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 5.9604643443123e-10, 0.0, 0.0, 0.0, 0.00079777417704463, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 4.2803883843589574e-05, 1.7881393032936899e-09, 0.0013778209686279297, 0.0, 0.0, 0.0, 0.0, 0.0, 0.11000756174325943, 4.822163227399942e-15, 1.3598142421377291e-14, 1.0312384728431139e-14, 0.006335214711725712, 6.922782490217504e-15, 9.295552168438453e-15, 7.032061598874571e-15, 0.000426163082011044, 8.673116783412208e-15, 0.11721887439489365, 0.10139776766300201, 1.1257403294056764e-14, 7.878227184390883e-15, 4.165590720533454e-15, 1.4020321429980727e-14, 8.316266037898708e-15, 1.4696445151335738e-14, 1.424453105111894e-14, 1.3773825524967306e-14, 0.0010909214615821838, 0.0022049075923860073, 1.4519232306242982e-14, 1.1718472126367487e-14, 1.2003068420381353e-14, 9.440311793190107e-15, 1.2111204034559626e-14, 1.4780464043439787e-14, 0.11635022610425949, 4.9156743942273956e-15, 1.1873251303852212e-14, 1.4121497821464359e-14, 5.953872089765151e-15, 4.581049369733374e-15, 9.829725026294905e-15, 1.3577329127797359e-14, 6.5723272669722475e-15, 1.0514059038007652e-14, 1.2612393429449996e-14, 8.211644763418593e-15, 1.3433299645446237e-14, 1.2383984218959296e-14, 1.518835445325599e-14, 5.087704244715902e-15, 6.037314575948593e-15, 9.24265241978358e-15, 1.0630642958801839e-14, 0.09807739406824112, 1.0123028819006546e-14, 1.3402823400004028e-14, 6.758037970108332e-15, 1.3642719224292443e-14, 5.724883508738529e-15, 0.1075160801410675, 1.091973276260089e-14, 1.401476150571495e-14, 5.832907738084238e-15, 1.5196386019661855e-14, 1.3269814663329632e-14, 7.0987713727014776e-15, 8.151120871205484e-15, 6.546949312839561e-15, 0.09998062252998352, 6.680898679601883e-15, 1.443163893510152e-14, 4.538533397978892e-15, 1.5270331995957155e-14, 7.49262221141694e-15, 1.127057719748541e-14, 9.279694864632905e-15, 9.29804583343517e-15, 9.665420116285357e-15, 1.2325370386042245e-14, 1.0487593493570691e-14, 4.926061982776049e-15, 1.2919237890856444e-14, 6.175487672502398e-15, 7.191849282176411e-15, 1.2820760146342765e-14, 6.823225202212549e-15, 1.4673282188360122e-14, 8.111139222029187e-15, 3.7610378058161587e-05, 1.4985373171841863e-14, 7.495642730906849e-15, 1.380788217867756e-14, 1.1483209572300552e-14, 0.06467266380786896, 4.140800183749689e-15, 0.11345454305410385, 0.0017273519188165665, 6.468737255105415e-15, 4.684016812383975e-15, 9.30341941045255e-15, 5.721441166840887e-15, 9.976146529689072e-15, 1.2974520343191943e-14, 5.040431759446113e-15, 9.34756846172934e-15, 9.93615725721625e-15, 1.1748713743683307e-14, 7.278878529375001e-15, 6.586485422685603e-15, 7.537386208613436e-15, 1.0377160726039465e-14, 0.0018187506357207894, 1.3650860057948504e-14, 9.919485107715443e-15, 2.8221745651535457e-06, 5.5660364555246145e-15, 1.5835745216463692e-05, 7.99608504273774e-15, 0.09729301184415817, 1.190403671632017e-14, 7.77687382651493e-05, 4.6562667424825035e-15, 1.4627325568773893e-14, 9.84003341726299e-15, 1.0256212044468076e-14, 4.148689025103942e-15, 8.958583827295852e-15, 3.879818321272325e-15, 1.3677334072714938e-14, 7.22814379693331e-15, 1.2930673682677325e-14, 6.532419733178835e-15, 6.436913380244123e-15, 5.321229534208018e-15, 4.776021107598264e-15, 3.923448141352447e-15, 1.4314902548376827e-14, 0.10561566799879074, 1.0774613148846653e-14, 1.3536799448304188e-14, 1.4783528608642953e-14, 1.3839944916829976e-14, 1.3042992792582087e-14, 0.10453756153583527, 9.525166706813096e-15, 1.2564727497376207e-14, 1.0448607955140365e-14, 5.551216767079453e-15, 4.387663701062219e-15, 4.369050999079253e-15, 1.4818168868053865e-14, 5.444854416376257e-15, 0.11138197034597397, 8.628638236318938e-15, 1.1652176551651787e-14, 9.506497253622664e-15, 1.3577523945375227e-14, 9.97335216799608e-15, 1.3830078677060358e-14, 7.330135881145148e-15, 1.3716217120158646e-14, 1.0833783482410049e-14, 0.11870888620615005, 4.945880859675905e-15, 4.490026785704954e-15, 0.1084272488951683, 8.459356160711324e-15, 6.598094432744197e-15, 9.762299509627568e-15, 1.261357080524668e-14, 0.08761802315711975, 5.485483198724257e-15, 7.349163629272269e-15, 1.1541992811807053e-14, 0.09255965799093246, 1.1372798827625954e-14, 0.09956346452236176, 1.1088082254933577e-14, 1.48739951155415e-14, 9.132750741910282e-15, 0.11155865341424942, 0.09809461236000061, 8.805840917016326e-15, 1.515160338774052e-14, 5.345909109675693e-15, 4.905489246553136e-15, 1.0244966835060328e-14, 1.0436444562017793e-14, 1.3073300478467793e-14, 1.205062085004021e-14, 1.1104439308178005e-14, 5.801794100349219e-15, 8.87032722935669e-15, 1.0711603214933352e-14, 5.15362712493481e-15, 9.927304915884495e-15, 0.0856390967965126, 0.0010330475633963943, 9.135750085576509e-15, 8.322908470271076e-15, 0.11705116182565689, 0.10282691568136215, 8.999207527446169e-15, 1.233218984830059e-14, 0.0001162262778962031, 1.04054541675766e-14, 9.847420391595994e-15, 9.515315713636528e-15, 1.0827013995095593e-14, 1.242384982462182e-14, 1.1623347785291987e-14, 1.1361840762387325e-14, 0.10984303057193756, 6.496022303918844e-15, 1.501648299792862e-14, 5.6657254571528676e-15, 1.2017872015200517e-14, 8.75918634228156e-15, 1.4949767294871082e-14, 1.160612337030957e-14, 1.1885214797199232e-14, 1.0626914319768026e-14, 1.3218922382759752e-14, 4.921186037615179e-15, 6.217637302507193e-15, 1.3687197771385714e-14, 0.08266463875770569, 1.3384052302859925e-14, 0.11765918135643005, 6.989851406014047e-15, 1.4316471253395142e-14, 1.3579699125983776e-14, 1.115908733283601e-14, 1.4187952638374142e-14, 8.580507283157107e-15, 1.3508785527639646e-14, 0.0822112038731575, 8.904294944607483e-15, 3.965165361037668e-15, 1.4748969664394977e-14, 0.007581762038171291, 5.2664976532882345e-15, 1.2072976590617093e-14, 0.0005355185130611062, 3.935965170730497e-15, 0.11404784023761749, 8.173658723866026e-15, 8.872103457447083e-15, 1.4085652234169504e-14, 5.1193964059538955e-15, 1.443760882331377e-14, 1.1218780285727863e-14, 1.030059402980536e-14, 0.10762296617031097, 5.487756211638214e-15, 1.0664453125924442e-14, 1.1801722759588375e-14, 5.9739560879774976e-15, 7.242472206269064e-15, 1.3967297167482608e-14, 1.3826599912745985e-14, 1.0125571611914203e-14, 1.3867673387391293e-14, 9.786304423352755e-15, 0.09221060574054718, 6.548709023787482e-15, 8.692153848901749e-15, 8.070829771102302e-15, 4.201236831569231e-15, 1.3476120549061731e-14, 0.0017287653172388673, 1.1659444941372176e-14, 4.858904128520044e-15, 1.1484923966985795e-14, 1.0626436593185774e-14, 6.7452846185379976e-15, 0.11231004446744919, 0.09344173967838287, 1.521901196374891e-14, 1.2167571536100558e-14, 9.490199492684544e-15, 5.97577085606699e-15, 1.3458581037822936e-14, 5.088263709977564e-15, 1.037241734153484e-14, 1.505874994199661e-14, 4.942742179089854e-15, 4.777053217244493e-15, 8.122970029944554e-06, 8.941656720877923e-15, 1.1599997628035028e-14, 9.353021659843763e-15, 4.485099595050775e-15, 4.290876210794785e-15, 7.905252617605978e-15, 9.148213328362409e-15, 6.523618213823915e-15, 1.1771049155469455e-14, 7.863570126271594e-15, 9.98356315017523e-15, 9.741985965486515e-15, 4.048802664798979e-15, 7.819587093452467e-15, 1.3078364041426479e-14, 8.121168092124677e-15, 8.125289754446017e-15, 3.254291296005249, 0.0, 6.334987640380859, 2.0708084106445312, 1.5216783285140991, -3.814697265625e-06, 3.8401830196380615, 2.2563133239746094, 0.0, 0.0, 0.0, 1.8505916595458984, 3.814697265625e-06, 1.93072509765625, 3.1312484741210938, 2.3863718509674072, 8.212482452392578, 0.0, 2.054041862487793, 7.266547679901123, 8.322410583496094, 2.0390841960906982, 3.693894624710083, 8.819988250732422, 2.8932759761810303, 1.2035408020019531, 0.8859139084815979, 1.7970774173736572, 3.207233190536499, 3.184680700302124, 3.4800567626953125, 1.362638235092163, 0.7836266756057739, 0.0, 0.0, 2.990680456161499, 3.1455676555633545, 0.0, 2.0795412063598633, 0.8037929534912109, 1.9687576293945312, 16.764652252197266, 0.786861777305603, 2.95803165435791, 0.6786673069000244, 10.645954132080078, 3.814697265625e-06, 2.6833105087280273, 3.3631362915039062, 2.6284821033477783, 3.2441256046295166, 3.373715400695801, 7.997581481933594, 2.1062889099121094, 2.842926502227783, 3.799266815185547, 2.590890645980835, 5.278144359588623, 1.7454497814178467, 1.5511927604675293, 2.6346511840820312, 9.890411376953125, 6.100852966308594, 0.8737305998802185, 2.6773288249969482, 3.8188934326171875, 2.2089970111846924, 3.1579577922821045, 2.786456823348999, 3.7320556640625, 0.0, 0.0, 2.995990514755249, 4.557918548583984, 1.2425479888916016, 4.112110614776611, 2.711711883544922, 3.6575546264648438, 0.0, 2.1566598415374756, 3.3107292652130127, 7.346850872039795, 3.2422475814819336, 3.4629592895507812, 4.082672119140625, 2.648432493209839, 0.8939469456672668, 1.6248154640197754, 0.0, 1.4443258047103882, 2.554252862930298, 4.576629638671875, 14.077587127685547, 10.9208984375, 1.9073486328125e-06, 10.27255916595459, 2.3678054809570312, 6.165985107421875, 0.6391066312789917, 18.74866485595703, 1.9868087768554688, 1.4231300354003906, 3.26590895652771, 1.6756319999694824, 2.2705001831054688, 5.2117919921875, 19.730499267578125, 2.769972801208496, 5.933265209197998, 2.5436348915100098, 1.6027709245681763, 1.6545653343200684, 0.0, 2.29547119140625, 6.92543363571167, 8.722174644470215, 3.5014636516571045, 2.465013027191162, 0.0, 0.0, 2.7039153575897217, 3.1977860927581787, 0.838366687297821, 1.950405478477478, 3.6193788051605225, 2.6113128662109375, 8.794562339782715, 3.094372510910034, 13.589848518371582, 2.0444488525390625, 0.9975571036338806, 3.918475866317749, 1.2996550798416138, 5.351531982421875, 3.6385154724121094, 2.612377166748047, 3.814697265625e-06, 2.1494407653808594, 2.337120294570923, 2.9394073486328125, 2.035797119140625, 3.0965576171875, 1.741741418838501, 2.280100107192993, 2.2820518016815186, 1.7358067035675049, 0.0, 2.7550811767578125, 2.235563039779663, 2.0754997730255127, 2.699317455291748, 2.5995702743530273, 1.9765061140060425, 0.0, 3.6007940769195557, 2.74929141998291, 4.422435283660889, 3.4441680908203125, 0.0, 2.6064605712890625, 2.0232009887695312, 3.303370952606201, 2.0660476684570312, 0.9612628221511841, 2.8422229290008545, 2.4499764442443848, 0.0, 3.3532533645629883, 6.827171325683594, 0.0, 2.0992698669433594, 2.883725166320801, 2.2149434089660645, 4.776824951171875, 1.9139753580093384, 1.7038042545318604, 0.0, 1.3376460075378418, 10.19516658782959, 3.0350325107574463, 0.0, 1.4624900817871094, 2.5676896572113037, 0.9194211959838867, 6.373668670654297, 1.5508918762207031, 3.9786834716796875, -3.814697265625e-06, 2.065135955810547, 4.640438079833984, 2.102801561355591, 3.131103515625, 0.0, 1.8714181184768677, 2.4938392639160156, 0.0, 5.420372009277344, 1.955889344215393, 0.0, 0.0, 1.3486645221710205, 5.433215618133545, 2.8793182373046875, 1.993559718132019, 3.4490087032318115, 3.2230606079101562, 27.954050064086914, 2.5589985847473145, 3.1901888847351074, 4.513010025024414, 2.9936349391937256, 4.137216567993164, 1.5195999145507812, 7.524329662322998, 14.009840965270996, 5.019015312194824, 2.057677984237671, 1.6901525259017944, 5.054710388183594, 3.230889320373535, 0.0, 1.9536770582199097, 0.9758619666099548, 3.7050323486328125, 6.76405668258667, 4.7206573486328125, 4.582744598388672, 2.2630956172943115, 2.1734371185302734, 2.903831720352173, 3.814697265625e-06, 2.561751365661621, 6.4259490966796875, 0.0, 3.299213171005249, 7.629394360719743e-08, 1.6128569841384888, 1.4025077819824219, 3.0275955200195312, 2.8444855213165283, 5.845241546630859, 2.789750337600708, 0.0, 2.043910264968872, 8.23919677734375, 0.0, 2.740999698638916, 2.182055950164795, 1.7394869327545166, 0.0, 2.28845477104187, 3.0122947692871094, -7.62939453125e-06, 2.955533027648926, -1.9073486328125e-06, 5.401409149169922, 0.0, 4.75316047668457, 0.745041012763977, 2.646437883377075, 2.462116241455078, 4.533191204071045, 6.1172637939453125, 3.814697265625e-06, 2.7246246337890625, 1.379644751548767, 2.3857250213623047, 4.5612030029296875, 7.629394360719743e-08, 3.2269134521484375, 2.6593739986419678, 6.620429515838623, 10.192436218261719, 3.2298412322998047, 1.4528295993804932, 0.0, 2.0308616161346436, 4.5423431396484375, 3.554443359375, 3.5334222316741943, 0.0, 2.236816644668579, 0.0, 0.0, 2.0481271743774414, 1.8688808679580688, 0.7673784494400024, 1.6048494577407837, 4.935462951660156, 1.604361891746521, 2.2337722778320312, 1.7780685424804688, 0.0, 2.9542465209960938, 0.0, 1.4713455438613892, 17.821086883544922, 5.4801483154296875, 1.9832197427749634, 0.0, 9.5367431640625e-07, 1.81605064868927, 9.5367431640625e-07, 1.7117103338241577, 1.2143800258636475, 9.5367431640625e-07, 9.5367431640625e-07, 0.993675947189331, 2.647142171859741, 9.5367431640625e-07, 0.4000368118286133, 9.5367431640625e-07, 1.4615745544433594, 9.5367431640625e-07, 1.264216423034668, 9.5367431640625e-07, 1.6005409955978394, 1.5071426630020142, 1.2490870952606201, 9.5367431640625e-07, 0.7185859680175781, 1.5808770656585693, 9.5367431640625e-07, 1.2337453365325928, 0.8435258269309998, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.5432186126708984, 9.5367431640625e-07, 9.5367431640625e-07, 2.4718964099884033, 1.6035757064819336, 1.552683711051941, 9.5367431640625e-07, 0.8858982920646667, 2.3230180740356445, 1.4028695821762085, 1.22013258934021, 1.604750633239746, 1.7478322982788086, 9.5367431640625e-07, 1.5027456283569336, 1.6317718029022217, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.4531017541885376, 0.9020547270774841, 1.6907157897949219, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.18175411224365234, 9.5367431640625e-07, 9.5367431640625e-07, 1.1192864179611206, 1.2499771118164062, 0.6224454045295715, 9.5367431640625e-07, 9.5367431640625e-07, 1.1638725996017456, 1.1087349653244019, 1.2449755668640137, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 2.480584144592285, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 2.711759567260742, 0.7770852446556091, 0.9478559494018555, 1.9353100061416626, 9.5367431640625e-07, 1.1227964162826538, 0.945692241191864, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.4639772176742554, 1.5542138814926147, 1.0004820823669434, 0.9459872841835022, 9.5367431640625e-07, 9.5367431640625e-07, 1.5534836053848267, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.9551454782485962, 1.9188590049743652, 9.5367431640625e-07, 1.0887932777404785, 9.5367431640625e-07, 9.5367431640625e-07, 1.5717906951904297, 9.5367431640625e-07, 9.5367431640625e-07, 1.139607310295105, 1.8005425930023193, 1.0351006984710693, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.3258247375488281, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.8958959579467773, 2.384629726409912, 0.8789120316505432, 1.3326623439788818, 9.5367431640625e-07, 9.5367431640625e-07, 1.5033042430877686, 9.5367431640625e-07, 1.1433734893798828, 1.280091404914856, 9.5367431640625e-07, 9.5367431640625e-07, 1.2395333051681519, 1.4884376525878906, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.1793628931045532, 9.5367431640625e-07, 9.5367431640625e-07, 1.3290787935256958, 1.9122693538665771, 9.5367431640625e-07, 9.5367431640625e-07, 1.163002848625183, 1.2169039249420166, 9.5367431640625e-07, 1.5071334838867188, 1.3282941579818726, 1.549864411354065, 1.7789901494979858, 1.1480791568756104, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.5262595415115356, 9.5367431640625e-07, 0.0, 1.0119707584381104, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.1761503219604492, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.1965916156768799, 0.31284427642822266, 9.5367431640625e-07, 1.9005651473999023, 9.5367431640625e-07, 0.38691702485084534, 1.0298881530761719, 1.1496175527572632, 9.5367431640625e-07, 1.4956527948379517, 1.2358478307724, 1.952000379562378, 9.5367431640625e-07, 1.027052879333496, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 2.7020468711853027, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.3884998857975006, 1.8954883813858032, 0.9224709272384644, 2.1862597465515137, 1.3412268161773682, 0.9735955595970154, 1.2621351480484009, 9.5367431640625e-07, 9.5367431640625e-07, 1.383089303970337, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 2.1137282848358154, 2.036484718322754, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.9998881816864014, 9.5367431640625e-07, 1.4865998029708862, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 2.1934149265289307, 9.5367431640625e-07, 1.2947720289230347, 1.6410115957260132, 9.5367431640625e-07, 1.170311450958252, 9.5367431640625e-07, 1.651373267173767, 0.0, 9.5367431640625e-07, 2.3462610244750977, 9.5367431640625e-07, 0.9809854030609131, 1.734686255455017, 1.072029948234558, 2.3064160346984863, 9.5367431640625e-07, 1.7371482849121094, 1.7936592102050781, 0.9239334464073181, 0.8032556176185608, 1.1039414405822754, 2.4042580127716064, 1.5597628355026245, 9.5367431640625e-07, 2.4848744869232178, 9.5367431640625e-07, 1.493762731552124, 2.544987678527832, 0.9070287346839905, 1.3511810302734375, 9.5367431640625e-07, 1.1751562356948853, 9.5367431640625e-07, 1.3500242233276367, 1.1353778839111328, 9.5367431640625e-07, 9.5367431640625e-07, 2.1829867362976074, 9.5367431640625e-07, 1.6045769453048706, 1.0866994857788086, 1.8979138135910034, 9.5367431640625e-07, 1.942989706993103, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 1.4158211946487427, 9.5367431640625e-07, 1.7142711877822876, 0.041731834411621094, 1.7860442399978638, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.9233429431915283, 1.323036789894104, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.2030208110809326, 1.1948728561401367, 2.0473029613494873, 1.1819555759429932, 1.433013916015625, 1.3009012937545776, 0.9744672775268555, 9.5367431640625e-07, 1.4424190521240234, 1.445988416671753, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.2636470794677734, 9.5367431640625e-07, 0.00930517166852951, 9.5367431640625e-07, 1.388680338859558, 1.5540844202041626, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 5.9604643443123e-10, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.005852407775819302, 0.0, 0.0, 0.0, 0.0, 0.0, 1.19209286886246e-09, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.00022025882208254188, 0.001159500447101891, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.00209750235080719, 0.0, 0.0, 0.0, 0.0, 0.0, 0.00013504743401426822, 0.0, 0.0, 0.0, 0.0004947781562805176, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 5.9604643443123e-10, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.01007551047950983, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 8.05258707714529e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.02021779492497444, 0.0, 0.0, 0.004842833150178194, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0001817941665649414, 0.0, 0.0033995043486356735, 2.9802320611338473e-09, 0.0, 0.0, 0.0, 0.0, 0.0010772001696750522, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.00017642974853515625, 0.0, 0.0, 0.0, 0.0008254765998572111, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.016344401985406876, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.00043207406997680664, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 5.9604643443123e-10, 0.0, 0.0, 0.0, 0.0, 0.04011679068207741, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0005346113466657698, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.006307606119662523, 8.237719157477841e-05, 0.0046377587132155895, 0.0, 0.0, 0.0020509595051407814, 0.0, 5.9604643443123e-10, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 3.5762786865234375e-07, 0.0, 0.01564735919237137, 0.0, 0.0, 0.0, 0.0, 1.19209286886246e-09, 0.0, 0.0, 0.0, 5.9604643443123e-10, 0.0, 0.0, 0.0, 0.0, 6.687607180544137e-15, 7.11810066455782e-15, 8.19281522100113e-15, 0.10983704030513763, 5.7558709385644065e-15, 5.2106743704159134e-15, 9.453029145860183e-15, 0.0011433534091338515, 1.4693111229655345e-14, 3.831656451407919e-15, 6.853160617117937e-15, 0.10079669952392578, 9.855627293821941e-15, 5.366157855796281e-15, 1.0860073691026928e-14, 1.0746190958301535e-14, 6.478699633114546e-15, 1.0724083398378197e-14, 1.3079827714359334e-14, 1.508384244602607e-14, 0.07837102562189102, 1.2566496949203022e-14, 8.350933402363932e-15, 0.00987568125128746, 1.143798478918075e-14, 0.11890917271375656, 6.353664017572655e-15, 3.944209342406123e-15, 1.272190462513461e-14, 1.1640328254785594e-14, 1.3685990749435877e-14, 7.397658806601419e-15, 0.09926354885101318, 0.07577592879533768, 1.439659718207361e-14, 1.429225796956493e-14, 0.10231427103281021, 1.1012587902410696e-14, 1.1817595309986974e-14, 1.0492225069726278e-14, 8.515063823586345e-15, 8.103833562859118e-15, 1.3117725662485386e-14, 8.146572508849204e-05, 0.11581172049045563, 9.092360822853408e-15, 0.1439138799905777, 0.11169356107711792, 4.3374007659721485e-15, 0.08576223999261856, 4.414616712960324e-15, 9.622323079929058e-15, 6.430811778408577e-15, 7.791529974107616e-15, 0.10420036315917969, 1.3408796676348065e-14, 6.336598844784323e-15, 9.770608902840133e-15, 1.4750778926770312e-14, 0.030539946630597115, 9.86708510849945e-15, 0.11615448445081711, 1.0807902390706694e-14, 1.282760078442479e-14, 1.0444500692379129e-14, 6.794856374743108e-15, 7.186858564051189e-15, 1.0654309059348124e-14, 1.1647627137692084e-14, 8.686656605074068e-15, 0.10727056115865707, 0.10327783226966858, 1.473003339582616e-14, 5.95031073973842e-15, 8.124538436221802e-15, 1.5198332501374645e-14, 7.164703570282805e-15, 0.09735694527626038, 0.10493353009223938, 1.4385197812669462e-14, 6.971360253259012e-15, 8.21136778364484e-15, 1.1068409067700648e-14, 1.049543278349753e-14, 9.922562378412818e-15, 4.7882548044554576e-15, 8.402487215665617e-15, 0.05093815177679062, 0.08758658915758133, 1.1280210503194534e-14, 1.5171313844423127e-14, 7.822630482831952e-15, 1.0524923082589135e-14, 1.1510251946174593e-14, 1.1338981037206826e-14, 1.1581625483409082e-14, 8.745912488965137e-15, 9.972123123189614e-15, 4.33845532199148e-15, 0.11173028498888016, 9.265124203874237e-15, 1.140102111839552e-14, 8.896466666108958e-15, 0.09690499305725098, 9.610636566355791e-15, 4.460303552552853e-15, 0.08776066452264786, 0.10473515093326569, 1.3917250225794087e-14, 1.0963413404657847e-14, 8.336230604465492e-15, 1.2048034858452242e-14, 0.09869495034217834, 7.491242394745863e-15, 1.1994131375754873e-14, 1.4768698755802424e-14, 5.999177119520027e-06, 1.3549677737234242e-14, 0.008110697381198406, 5.093513196668172e-15, 1.0880512596044174e-14, 9.407994945153514e-15, 5.490858469807533e-15, 6.067073384484478e-15, 1.4188703956598357e-14, 0.09190284460783005, 7.631522909272437e-15, 5.35708528589824e-15, 1.0024136028348712e-14, 9.592893767209655e-15, 1.2757795952208616e-14, 6.985967759950886e-15, 9.115721991538681e-15, 9.365308719776633e-15, 0.11460145562887192, 1.306387046066601e-14, 0.018367106094956398, 5.2284544390117284e-15, 0.011320391669869423, 0.09976383298635483, 1.0662715014316676e-14, 1.417663458413293e-14, 0.098521888256073, 1.0489228267158892e-14, 0.1151324063539505, 5.052367724222347e-15, 1.0319955508913698e-14, 0.10354141145944595, 1.2232743098095251e-14, 0.11761846393346786, 1.0529920576977936e-14, 0.08694563060998917, 7.376194991717995e-15, 0.1177632212638855, 6.585208944034091e-15, 6.2985776533644455e-15, 1.2625806196169768e-14, 4.920846800919804e-15, 9.211030985796682e-15, 5.4938425668807096e-15, 5.557946443845389e-15, 1.2079801982106068e-14, 3.938001014419223e-15, 6.248130065091874e-15, 0.10325994342565536, 1.4246140413718723e-14, 0.08972643315792084, 1.1605843849436977e-14, 4.109182561411054e-15, 5.930358031632898e-15, 1.2930688929270375e-14, 0.10901939123868942, 1.1390488263696413e-14, 8.620211105526705e-15, 6.305416173864103e-15, 1.4285800190375064e-14, 5.373893384187081e-15, 0.10845538228750229, 0.11595698446035385, 1.4720116334079707e-14, 0.10515524446964264, 1.493146460694681e-14, 5.0928825806389414e-15, 8.2777218036339e-15, 0.0966697484254837, 6.316176880426022e-15, 0.11851539462804794, 7.626599953782995e-15, 1.3676812300419429e-14, 1.3611489966560125e-14, 1.3495502356960804e-14, 1.1908632717091971e-14, 0.21265742182731628, 0.08180347084999084, 4.962473388079669e-15, 7.674757164966191e-15, 0.0006139492616057396, 5.893458311835185e-15, 1.0329786173299531e-14, 1.0779502223018204e-14, 0.01661588065326214, 5.27943565804107e-15, 1.476253066188052e-14, 0.10937167704105377, 1.1910626632649808e-14, 8.279176159204336e-15, 4.605603584324856e-15, 5.9265794176551964e-15, 1.3103133825903036e-14, 1.0364554334685479e-14, 1.512887918783158e-14, 1.4909590828116916e-14, 1.1169505838087238e-14, 5.1051137363972935e-15, 1.1145769433806331e-14, 9.32293504955729e-15, 1.3941440639734723e-14, 6.0814932733785354e-15, 0.10350769758224487, 1.4810440539443116e-14, 7.570053728290192e-15, 7.035399332203226e-15, 0.09457019716501236, 4.435668022798435e-15, 7.910374625838025e-15, 4.382553974807907e-15, 1.2607436592642664e-14, 0.11352191865444183, 7.431943312174484e-15, 9.641946292218099e-15, 5.468034743527292e-15, 5.146873307729878e-15, 1.3025605747273798e-14, 0.08661113679409027, 4.5571943808398515e-15, 0.10098989307880402, 9.964553189740002e-15, 0.11583217233419418, 1.1423998581155687e-14, 1.4463439940073236e-14, 1.5060672706786876e-14, 1.0017594392897067e-14, 7.667860622709646e-15, 0.11499633640050888, 1.5070960768964227e-14, 8.55644985338919e-15, 5.178210138646498e-15, 4.584692881955989e-15, 5.923215426305176e-15, 1.2028624251432963e-14, 1.259683766937367e-14, 1.417566303734243e-14, 5.074385922169749e-15, 0.10733570158481598, 8.036890007938769e-15, 9.208445841241662e-15, 0.1013127937912941, 0.08842132985591888, 0.09838434308767319, 7.317288085401195e-15, 9.168305796904228e-15, 5.840891870645057e-15, 0.11432000994682312, 0.012575607746839523, 0.023102812469005585, 1.424442601903348e-14, 7.21313267904207e-15, 5.9281354171793026e-15, 5.971625053306654e-15, 6.1741171731937404e-15, 4.488567771453308e-15, 4.8208117863325975e-15, 0.0003602808283176273, 1.30184788120556e-14, 1.0172021204675735e-14, 1.3498563534032181e-14, 0.09901628643274307, 1.3648246961306225e-14, 4.754725005238396e-15, 1.0717123328650609e-14, 1.1610364464276473e-14, 1.183543043572436e-14, 6.054997235755474e-15, 1.1555767261595302e-14, 5.53580839073595e-15, 0.03416778892278671, 0.08629922568798065, 6.281883057490537e-15, 4.687680653397324e-15, 8.13008904312516e-15, 8.505930267316102e-15, 8.560912022955326e-15, 1.2293244120418784e-14, 0.022984780371189117, 5.338702553360454e-15, 0.11189335584640503, 1.0477969505223988e-14, 1.0300527961235473e-14, 0.10380758345127106, 0.0006111146649345756, 5.627647399902344, 7.220718860626221, 1.9594979286193848, 3.0361785888671875, 3.12020206451416, 5.120944023132324, 6.170623779296875, 5.320884704589844, 0.0, 4.402076721191406, 11.333353042602539, 8.606842041015625, 3.839830160140991, 3.0137557983398438, 10.25839900970459, 3.017348051071167, 7.558539867401123, 4.993596076965332, 2.8529436588287354, 2.8154830932617188, 0.9074398875236511, 3.6421926021575928, 0.0, 2.319382905960083, 1.6346100568771362, 2.444568634033203, 0.0, 3.958505153656006, 2.1800622940063477, 4.997999668121338, 2.055004119873047, 4.311256408691406, 3.7177505493164062, 12.566940307617188, 1.5142263174057007, 2.008960723876953, 2.5594329833984375, 5.917901515960693, 1.5745642185211182, 4.907049655914307, 7.9728546142578125, 0.0, 7.82647705078125, 7.9822235107421875, 7.811282634735107, 6.783935546875, 4.967823028564453, 3.3105080127716064, 8.540139198303223, 2.666142463684082, 3.7941277027130127, 1.4482688903808594, 8.901251792907715, 1.3880761861801147, 1.0066146850585938, 1.0844841003417969, 2.781846046447754, 0.0, 4.024753093719482, 1.5407752990722656, 22.67107391357422, 1.6794909238815308, 3.7184677124023438, 2.8396999835968018, 2.666259765625, 4.17303991317749, 3.584477424621582, 6.0448455810546875, 3.7176780700683594, 2.0867347717285156, 2.0597143173217773, 9.50205135345459, 1.2517852783203125, 6.2715606689453125, 7.640923976898193, 4.3295578956604, 2.1406021118164062, 2.6985366344451904, 6.4876251220703125, 2.2423388957977295, 6.8651123046875, 1.789597988128662, 7.115570068359375, 4.029399871826172, 7.112730503082275, 3.14111328125, 0.0, 3.0806808471679688, 10.150650024414062, 4.970109939575195, 0.0, 3.683361053466797, 8.686126708984375, 0.0, 2.0872576236724854, 3.622296094894409, 1.6783697605133057, 2.0594160556793213, 2.613037586212158, 2.1060333251953125, 2.5207080841064453, 3.684983730316162, 1.1558456420898438, 3.3701257705688477, 3.9177632331848145, 6.402801513671875, 0.0, 2.934105396270752, 3.1690025329589844, 2.092578172683716, 5.978832244873047, 4.2884650230407715, 3.5937347412109375, 7.475555419921875, 3.4337282180786133, 1.3406853675842285, 3.1405868530273438, 5.48065185546875, 2.8501663208007812, 0.0, 0.9185702204704285, 3.04335618019104, 3.085026264190674, 0.0, 2.001939058303833, 1.1998252868652344, 4.933502197265625, 2.637451410293579, 0.0, 6.544124603271484, 4.565532684326172, 3.9248416423797607, 8.567877769470215, 3.1946184635162354, 4.577362060546875, 2.1680710315704346, 1.3690261840820312, 4.553497314453125, 2.8186681270599365, 3.6214115619659424, 6.187126159667969, 4.464085102081299, 2.1466939449310303, 6.365653991699219, 5.128509998321533, 3.704407215118408, 2.7868728637695312, 2.706500291824341, 3.5619020462036133, 2.9314422607421875, 2.0061581134796143, 4.139939785003662, 0.0, 4.440759658813477, 2.0143280029296875, 4.830625534057617, 4.760257244110107, 0.0, 1.8847473859786987, 2.7037389278411865, 2.579665422439575, 0.0, 6.75335693359375, 3.9673702716827393, 0.0, 4.977941036224365, 3.1840667724609375, 9.36637020111084, 3.7476730346679688, 13.215033531188965, 0.0, 6.2325286865234375, 5.0077033042907715, 0.0, 7.778235912322998, 7.938640117645264, 3.2913818359375, 3.519122838973999, 8.55325984954834, 0.0, 0.0, 4.161617279052734, 10.625441551208496, 1.9709968566894531, 6.121772289276123, 4.6329803466796875, 3.3916125297546387, 11.303924560546875, 3.402172088623047, 0.0, 1.953335165977478, 3.068528652191162, 2.4301140308380127, 1.0, 1.7647781372070312, 1.9203405380249023, 4.554542541503906, 7.689615249633789, 0.0, 4.3897552490234375, 2.246955633163452, 3.2148919105529785, 3.0394792556762695, 4.199132919311523, 6.4873504638671875, 2.1713027954101562, 3.086116075515747, 2.161329507827759, 12.388157844543457, 3.0731847286224365, 2.7141661643981934, 3.5677578449249268, 8.924511909484863, 10.78433609008789, 0.0, 4.33758544921875, 4.90842866897583, 2.2134742736816406, 2.8686227798461914, 2.740753173828125, 4.165120601654053, 3.932281494140625, 9.590850830078125, 21.435829162597656, 4.296172618865967, 2.3483452796936035, 2.6300926208496094, 4.9131622314453125, 4.116935729980469, 9.309638023376465, 2.431353807449341, 2.9982945919036865, 1.8043049573898315, 4.872682571411133, 3.895153045654297, 2.619248628616333, 3.2749955654144287, 1.7957149744033813, 5.408790111541748, 1.6706204414367676, 3.9316961765289307, 2.5970940589904785, 2.7384562492370605, 0.0, 5.149223327636719, 1.9552626609802246, 3.3263626098632812, 2.9676146507263184, 5.094611167907715, 0.0, 15.235313415527344, 3.974066734313965, 8.52786922454834, 3.2661633491516113, 0.0, 0.0, 2.39617919921875, 4.056041717529297, 10.518534660339355, 4.358039855957031, 4.013523578643799, 3.2187743186950684, 9.21109390258789, 5.822021484375, 2.7005271911621094, 4.419801712036133, 2.781524658203125, 0.0, 0.0, 5.983767032623291, 2.207326889038086, 3.396254777908325, 2.116497278213501, 2.9831433296203613, 2.942308187484741, 1.8963640928268433, 2.073740243911743, 8.654314041137695, 2.210876703262329, 1.7659187316894531, 3.205853223800659, 7.019416332244873, 0.0, 18.48965072631836, 3.9926023483276367, 7.181488037109375, 6.457892894744873, 14.710350036621094, 4.41204833984375, 2.03399658203125, 2.3423681259155273, 2.5747289657592773, 1.9766945838928223, 12.355841636657715, 7.2922515869140625, 6.020026683807373, 1.9520822763442993, 1.839141845703125, 3.4455108642578125, 3.2838234901428223, 9.5367431640625e-07, 1.4329321384429932, 1.9690698385238647, 1.6475210189819336, 9.5367431640625e-07, 0.9900546073913574, 0.1004018783569336, 0.9038259983062744, 9.5367431640625e-07, 0.7354040145874023, 1.0835037231445312, 0.0, 1.622469186782837, 0.9127572178840637, 9.5367431640625e-07, 1.7619314193725586, 1.2786614894866943, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 1.664123773574829, 9.5367431640625e-07, 9.5367431640625e-07, 0.9181298613548279, 1.1932051181793213, 1.2414482831954956, 2.3833706378936768, 9.5367431640625e-07, 1.361541986465454, 1.9383550882339478, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 1.3875550031661987, 0.9773855209350586, 2.206439971923828, 1.7225922346115112, 1.3843793869018555, 9.5367431640625e-07, 0.9053763151168823, 1.3036850690841675, 0.8601447939872742, 1.67961847782135, 0.12460843473672867, 9.5367431640625e-07, 1.7060527801513672, 1.7139430046081543, 1.2670129537582397, 9.5367431640625e-07, 9.5367431640625e-07, 0.8024734258651733, 1.6379555463790894, 1.3922195434570312, 1.488252878189087, 0.6216896176338196, 1.3893628120422363, 1.8772042989730835, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.3356962203979492, 1.5778379440307617, 9.5367431640625e-07, 9.5367431640625e-07, 1.5409890413284302, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.7181777954101562, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.9552297592163086, 0.8025544285774231, 9.5367431640625e-07, 0.19848383963108063, 9.5367431640625e-07, 1.2967995405197144, 1.174103856086731, 9.5367431640625e-07, 1.3833669424057007, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.1922607570886612, 9.5367431640625e-07, 1.0086263418197632, 9.5367431640625e-07, 9.5367431640625e-07, 2.564521312713623, 9.5367431640625e-07, 1.2667410373687744, 1.4577367305755615, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.4114526510238647, 1.509363055229187, 9.5367431640625e-07, 9.5367431640625e-07, 1.2684532403945923, 2.0566446781158447, 0.9816598296165466, 9.5367431640625e-07, 9.5367431640625e-07, 0.780911386013031, 1.1070302724838257, 9.5367431640625e-07, 1.0582183599472046, 1.02898108959198, 9.5367431640625e-07, 0.0, 0.9948434233665466, 9.5367431640625e-07, 1.9419883489608765, 9.5367431640625e-07, 9.5367431640625e-07, 0.8277940154075623, 9.5367431640625e-07, 0.24176311492919922, 1.5952303409576416, 2.395763635635376, 2.343506336212158, 9.5367431640625e-07, 1.4551806449890137, 9.5367431640625e-07, 1.222041130065918, 9.5367431640625e-07, 1.7349926233291626, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 2.325941562652588, 1.724324345588684, 9.5367431640625e-07, 2.117534637451172, 9.5367431640625e-07, 1.610619068145752, 9.5367431640625e-07, 1.5277132987976074, 0.8876304626464844, 2.1257071495056152, 2.1273767948150635, 1.3315191268920898, 1.1827411651611328, 1.3293050527572632, 1.1245590448379517, 1.9428846836090088, 2.7056710720062256, 1.0668609142303467, 1.6673064231872559, 0.04820365831255913, 1.4968308210372925, 9.5367431640625e-07, 2.434623956680298, 9.5367431640625e-07, 0.09608745574951172, 9.5367431640625e-07, 9.5367431640625e-07, 0.014199256896972656, 9.5367431640625e-07, 0.9349362254142761, 1.6282539367675781, 1.6758028268814087, 1.6972222328186035, 0.803033709526062, 1.6052072048187256, 9.5367431640625e-07, 9.5367431640625e-07, 1.930001139640808, 9.5367431640625e-07, 1.5841530561447144, 1.5417885780334473, 9.5367431640625e-07, 1.1196335554122925, 0.931666374206543, 9.5367431640625e-07, 1.5295753479003906, 2.3350560665130615, 1.4028576612472534, 9.5367431640625e-07, 1.7789804935455322, 1.5892075300216675, 9.5367431640625e-07, 2.4529471397399902, 1.607348918914795, 9.5367431640625e-07, 2.2343833446502686, 0.9450663328170776, 1.476452350616455, 1.3047915697097778, 0.24907398223876953, 0.9484692215919495, 2.4538650512695312, 1.1978249549865723, 0.03992176055908203, 9.5367431640625e-07, 1.3334957361221313, 1.6586875915527344, 0.9508904814720154, 9.5367431640625e-07, 9.5367431640625e-07, 0.9583024382591248, 1.3254708051681519, 9.5367431640625e-07, 9.5367431640625e-07, 1.612013816833496, 1.8496074676513672, 0.9477912783622742, 9.5367431640625e-07, 1.6322133541107178, 9.5367431640625e-07, 1.0524096488952637, 9.5367431640625e-07, 9.5367431640625e-07, 1.3427751064300537, 1.7574526071548462, 1.2083638906478882, 9.5367431640625e-07, 1.2478222846984863, 1.5103192329406738, 1.2835625410079956, 2.051165819168091, 0.16903209686279297, 0.7428063750267029, 1.4056676626205444, 1.094826579093933, 9.5367431640625e-07, 0.8415288925170898, 0.9239148497581482, 9.5367431640625e-07, 1.2035263776779175, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 0.9425125122070312, 9.5367431640625e-07, 1.3015193939208984, 9.5367431640625e-07, 1.0124845504760742, 1.533900260925293, 1.6342617273330688, 9.5367431640625e-07, 9.5367431640625e-07, 1.0848816633224487, 0.9389114379882812, 2.6568541526794434, 2.0490469932556152, 3.109822988510132, 9.5367431640625e-07, 1.5221375226974487, 1.1870583295822144, 9.5367431640625e-07, 9.5367431640625e-07, 1.8570436239242554, 9.5367431640625e-07, 9.5367431640625e-07, 2.9074339866638184, 9.5367431640625e-07, 1.0581111907958984, 1.3262914419174194, 9.5367431640625e-07, 9.5367431640625e-07, 2.2943148612976074, 9.5367431640625e-07, 9.5367431640625e-07, 1.5381460189819336, 0.08180772513151169, 9.5367431640625e-07, 1.9322961568832397, 0.8224912881851196, 1.21138334274292, 9.5367431640625e-07, 9.5367431640625e-07, 0.8418121337890625, 9.5367431640625e-07, 9.5367431640625e-07, 1.6734195947647095, 1.3738577365875244, 1.860543131828308, 0.0015707015991210938, 1.1135389804840088, 1.7557401657104492, 1.3167656660079956, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.724290370941162, 9.5367431640625e-07, 0.921504020690918, 1.5855072736740112, 1.8284729719161987, 9.5367431640625e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0016307162586599588, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 3.3795833587646484e-05, 0.0, 0.0, 0.0, 0.0, 0.013377964496612549, 0.0, 0.0, 0.0, 0.0, 0.0040684472769498825, 0.0, 0.0, 0.0, 0.0, 2.7365087589714676e-05, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.011910905130207539, 0.001087356242351234, 0.0002288973337272182, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0022672086488455534, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.002161740092560649, 0.0, 0.0, 0.0, 0.0, 0.0307198166847229, 0.0, 0.0, 0.0, 0.0, 0.022262215614318848, 0.0, 0.0, 0.0, 0.0005523562431335449, 0.0, 0.0, 0.0, 0.0, 0.0017666274216026068, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.38418573772492e-09, 0.0013812780380249023, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.010641233995556831, 0.0, 0.05759914591908455, 0.0, 0.0, 0.0, 0.0, 0.0, 1.19209286886246e-09, 0.0, 0.0, 0.0, 0.0, 0.00037300644908100367, 0.0, 0.0, 0.0, 2.325177092643571e-06, 0.0, 0.0, 0.009762169793248177, 0.0, 0.00176795304287225, 0.0, 0.0, 0.0, 0.0, 0.0012843012809753418, 0.0, 0.0, 0.0, 0.0, 6.020069065471034e-08, 1.7762184256753244e-07, 0.0, 0.0, 0.0, 0.0, 0.0343000628054142, 0.050831735134124756, 0.0, 0.0, 0.0, 0.0, 0.0, 0.00836226250976324, 0.0, 0.0, 0.0, 0.0, 4.839897155761719e-05, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.011267168447375298, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.010892736725509167, 0.0, 0.0, 0.0, 0.0, 0.0, 1.6403197378167533e-06, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 7.21615506336093e-05, 0.0, 0.004802703857421875, 0.0, 0.0, 0.0, 0.0008417564677074552, 0.0, 0.0, 0.0, 0.0, 0.0002514552907086909, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0005679130554199219, 0.0, 0.0, 0.0, 0.00019979476928710938, 4.2554140236461535e-05, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.1159648895263672e-05, 0.009641914628446102, 0.0, 0.0, 0.0, 0.0031048315577208996, 0.0, 0.0, 0.0, 5.9604643443123e-10, 0.0, 5.9604643443123e-10, 0.0024987459182739258, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0092019559815526, 0.00785553827881813, 0.0, 0.0, 0.0, 0.0, 0.00042515993118286133, 1.2824534678657074e-05, 0.0, 0.0, 0.0, 0.0, 0.0031196479685604572, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0034317784011363983, 0.0, 1.3005505655435453e-14, 0.11187158524990082, 0.059242524206638336, 1.2376521011661038e-14, 0.11143741011619568, 1.2374057839850423e-14, 0.10317245125770569, 8.239767104300383e-15, 0.11586751788854599, 0.11628232896327972, 0.11605991423130035, 1.3321460803222569e-14, 8.694608550382892e-15, 5.100357222881987e-15, 0.11346647888422012, 6.571122786121252e-15, 0.005079319234937429, 4.312463692488508e-15, 7.647712249993308e-15, 8.046973088142884e-15, 0.21659567952156067, 0.00010723926243372262, 0.1026441678404808, 0.0001148716255556792, 9.33267423438482e-15, 0.1012987494468689, 0.1088210716843605, 1.458676285499578e-14, 9.936573150393351e-15, 0.11651592701673508, 1.321726643334787e-14, 0.09547118842601776, 4.6759035072987e-15, 7.206595278755161e-15, 1.3117972149073037e-14, 1.3055800777777519e-14, 0.16634269058704376, 4.298672302041314e-15, 7.571945152861411e-15, 0.09840045124292374, 4.179401592738436e-15, 4.249049723859368e-15, 0.009027170017361641, 0.09980986267328262, 0.09907859563827515, 0.07311892509460449, 7.082329192645851e-15, 0.0035094639752060175, 1.3745187341020638e-14, 0.11626505851745605, 5.6176830189340245e-15, 0.09243753552436829, 0.014072895981371403, 0.10151239484548569, 1.2344923294596664e-14, 0.1008080467581749, 1.1448899655739069e-14, 1.268382710602374e-14, 1.3571099200470303e-14, 0.1016051173210144, 1.2978697909687802e-14, 6.651001381179121e-15, 1.1960857380487883e-14, 9.74384181467395e-15, 7.057699592122064e-15, 0.022838881239295006, 8.731135152167339e-15, 1.2721836015465882e-14, 0.11065574735403061, 1.2547840201506798e-14, 0.10927899926900864, 0.11815736442804337, 9.989292481030459e-15, 0.23596683144569397, 8.714485025523161e-15, 1.1450918135252376e-14, 0.09985797852277756, 0.001448108465410769, 0.09240026026964188, 1.0133093264485821e-14, 0.10800658911466599, 9.285562261858536e-15, 9.717484690454237e-15, 0.11492999643087387, 1.4039125561409772e-14, 1.4802065077660666e-14, 0.06631261855363846, 2.82367977888498e-06, 0.11710727214813232, 1.164429999227527e-14, 6.6712984081777026e-15, 4.044940194559499e-15, 0.10431716591119766, 0.03554222360253334, 1.4648619977067866e-14, 8.262499774538794e-15, 1.4425669046889272e-14, 1.3715948610714367e-14, 0.00020018310169689357, 1.4748251380455706e-14, 6.008767024527281e-15, 4.630693970771949e-15, 0.11745119839906693, 1.0487255527424737e-14, 4.578598479900494e-15, 1.1481896671232308e-14, 4.05366717501506e-15, 7.391088372029567e-15, 0.09618876874446869, 0.10887540876865387, 1.3540182497895521e-14, 1.3000032975563243e-14, 0.08227536827325821, 0.11287549883127213, 1.3586002745177243e-14, 0.031488459557294846, 1.2524314708429757e-14, 9.541675378955082e-15, 1.2539186065884701e-14, 1.0796146420431751e-14, 8.647942117186863e-15, 1.3741041114743828e-14, 4.329760105271441e-15, 0.0012620672350749373, 0.11187311261892319, 1.4770152264339913e-14, 6.040133925113529e-15, 0.08995820581912994, 0.09661614894866943, 0.03587338700890541, 4.382703052606624e-15, 4.56242989148683e-15, 5.2382037882346254e-15, 0.026248058304190636, 0.11328331381082535, 0.07580709457397461, 0.11470247060060501, 0.11522094160318375, 9.474542088654548e-15, 0.10150667279958725, 1.407771299435489e-14, 0.2303358018398285, 0.08599446713924408, 0.006083418615162373, 0.07982354611158371, 0.00031806089100427926, 0.012540278024971485, 6.309465414868452e-15, 1.4032349297831738e-14, 0.099162258207798, 0.03466042876243591, 7.768383104757998e-15, 1.509194008100182e-14, 1.439678861151969e-14, 0.19450631737709045, 4.070485014182794e-15, 0.005998848471790552, 9.079563002053342e-15, 9.935353422949305e-15, 1.8533668480813503e-05, 0.00029896345222368836, 0.11888481676578522, 0.1049286276102066, 0.07113254070281982, 6.157354391167578e-15, 1.0396290965153203e-14, 6.136027372105135e-15, 0.10433255881071091, 6.846028599702056e-15, 8.063107371722184e-15, 7.093006466462465e-15, 4.198776200857457e-15, 1.2964837062538932e-14, 6.975315473606216e-15, 0.11323972791433334, 1.4552452938434296e-14, 0.10211791843175888, 0.05258479341864586, 4.464519235531338e-15, 1.4079767896284928e-14, 0.09547624737024307, 6.612561331966827e-15, 0.003928793128579855, 0.10676227509975433, 0.10060039907693863, 7.107162081076979e-15, 0.048369068652391434, 0.08203341066837311, 0.11792340874671936, 0.11790359020233154, 4.596716938158737e-15, 0.11462518572807312, 0.07738557457923889, 0.11871206015348434, 6.376499602314158e-15, 0.09401914477348328, 8.018356927052845e-15, 0.10306189209222794, 0.11684790998697281, 8.460651274087676e-15, 3.93068900250205e-15, 0.001004360499791801, 7.820707718041685e-15, 1.4832214368385235e-14, 5.7691041342993604e-15, 5.683794363983696e-15, 0.11241720616817474, 0.00018431953503750265, 0.0927305594086647, 0.09246718883514404, 0.09526201337575912, 0.10655525326728821, 1.498509365096927e-14, 8.59049549567113e-15, 0.09444840252399445, 0.0003232246090192348, 1.4480414480336212e-14, 9.829389601247792e-15, 0.08907655626535416, 0.11142051219940186, 0.09452428668737411, 0.01687329262495041, 0.0010003262432292104, 1.3316426886417036e-14, 4.090386900311481e-15, 9.66493815453837e-15, 7.798903395913465e-15, 7.341493745934881e-15, 6.6991971323614175e-15, 1.3305170665580974e-14, 9.474320166022367e-15, 0.07943977415561676, 0.04232814162969589, 8.961202006135816e-15, 5.9408790278707435e-15, 1.1934833987249389e-14, 9.99696744656553e-15, 6.351477402019318e-15, 0.10003826022148132, 0.060723695904016495, 7.39628576619392e-15, 8.545049636952094e-15, 0.09983430802822113, 6.1068292993803324e-15, 6.586025907311718e-15, 1.1349297051471436e-14, 0.09002763777971268, 4.4365967944250996e-15, 0.1072099581360817, 8.929544856073335e-05, 1.2844129785357511e-14, 0.11455298215150833, 0.0001025657620630227, 1.4260429859538903e-14, 0.0941307321190834, 0.07440529018640518, 0.10903402417898178, 0.0011580202262848616, 1.383282052271062e-14, 0.004457682836800814, 1.3564288208541431e-14, 5.654812284660443e-15, 1.2632047981958085e-14, 8.648833195847375e-15, 9.211910205995932e-15, 1.0401789903046778e-14, 7.999528231668329e-15, 0.0023921781685203314, 1.3278186736980294e-14, 0.08342992514371872, 1.0893709369362396e-14, 1.1508636654344179e-14, 0.10710658878087997, 0.11298500001430511, 1.1345403241012908e-14, 5.296047668202622e-15, 6.836220381689325e-15, 7.563041989552821e-15, 1.4563710006303306e-14, 0.017930008471012115, 0.03674706444144249, 5.021883431967139e-15, 7.966800572652318e-15, 0.00012225640239194036, 1.2363452987350799e-14, 0.016335265710949898, 5.872949103083317e-15, 1.0370983314755139e-14, 0.00136185169685632, 3.901942821854607e-15, 1.3082336625949102e-14, 4.120502733234634e-15, 5.521981424904971e-15, 1.504800448202774e-14, 0.01889520324766636, 0.01573052443563938, 0.11549397557973862, 0.10434640944004059, 0.009089577943086624, 0.0007556123891845345, 3.881718635559082, 10.448431968688965, 2.843424081802368, 3.48451828956604, 6.119524955749512, 0.8526649475097656, 3.2440333366394043, 4.207424163818359, 3.8923721313476562, 5.026641845703125, 2.777440071105957, 1.639373779296875, 2.854069232940674, 3.4795455932617188, 3.9630751609802246, 7.128390789031982, 4.794197082519531, 4.410423278808594, 10.173529624938965, 2.9664244651794434, 0.0, 5.48834228515625, 11.369529724121094, 0.0, 2.583139657974243, 3.421680212020874, 4.66011381149292, 16.92153549194336, 2.5705950260162354, 0.0, 3.7040727138519287, 12.647445678710938, 3.5786056518554688, 2.9627110958099365, 3.519580841064453, 5.589999675750732, 0.0, 3.0390472412109375, 8.163580894470215, 3.9918088912963867, 2.4842987060546875, 5.417167663574219, 0.0, 4.375030517578125, 2.9833920001983643, 10.375999450683594, 3.4138004779815674, 7.4079132080078125, 3.485548257827759, 15.430468559265137, 6.6468963623046875, 5.254459857940674, 3.859955310821533, 4.622474670410156, 25.745946884155273, 5.322277545928955, 2.011925220489502, 4.738655090332031, 5.544737339019775, 3.614628314971924, 5.552570819854736, 7.216037273406982, 7.776504993438721, 3.2877087593078613, 3.0205612182617188, 1.437351942062378, 0.9554402232170105, 4.229249000549316, 9.471137046813965, 3.2047805786132812, 5.198678493499756, 5.178808689117432, 17.1392822265625, 6.277287483215332, 0.0, 0.0, 4.290718078613281, 2.1529769897460938, 4.189489364624023, 2.0773773193359375, 8.87235164642334, 2.4992284774780273, 3.0830764770507812, 1.6012243032455444, 6.518509387969971, 6.341706275939941, 1.6110687255859375, 2.9461135864257812, 7.2506842613220215, 2.411785125732422, 9.83011531829834, 13.04513168334961, 4.3240509033203125, 8.459197998046875, 9.618303298950195, 1.992545485496521, 3.5242691040039062, 7.324306488037109, 3.5478641986846924, 3.268815755844116, 6.455909252166748, 4.6314239501953125, 2.596043109893799, 6.260781288146973, 2.5460970401763916, 1.809285283088684, 1.3889083862304688, 5.561316013336182, 3.003208637237549, 4.240828990936279, 3.476487398147583, 4.985220432281494, 5.640037536621094, 13.677055358886719, 4.10417366027832, 2.9804039001464844, 9.073577880859375, 3.908946990966797, 7.1747727394104, 6.0545654296875, 0.0, 5.040709018707275, 3.5331950187683105, 18.40100860595703, 3.8761444091796875, 11.464874267578125, 4.931027412414551, 5.6032867431640625, 10.652419090270996, 0.8407803773880005, 11.503692626953125, 14.353886604309082, 5.063884735107422, 3.554459571838379, 3.86871337890625, 3.8432235717773438, 6.4466094970703125, 6.154242992401123, 10.247665405273438, 3.230025053024292, 4.325218200683594, 3.668734550476074, 3.106157064437866, 1.8314143419265747, 5.8153228759765625, 2.8428215980529785, 4.2423481941223145, 0.0, 3.5636520385742188, 4.29971170425415, 4.129495620727539, 0.0, 3.046314001083374, 2.6731042861938477, 0.0, 2.5114121437072754, 4.8213701248168945, 11.533378601074219, 0.0, 4.354248046875, 3.6677932739257812, 6.2070183753967285, 7.741189479827881, 3.9404072761535645, 0.0, 5.4092254638671875, 9.58233642578125, 14.813774108886719, 2.4150123596191406, 7.43145751953125, 5.499421119689941, 3.1263673305511475, 13.087028503417969, 4.586909770965576, 4.014477252960205, 18.14270782470703, 4.811225891113281, 3.0417871475219727, 9.655113220214844, 3.671600341796875, 3.4037420749664307, 2.9630322456359863, 5.7367095947265625, 1.3027076721191406, 4.046688556671143, 4.2455854415893555, 7.335364818572998, 0.8412296175956726, 3.8517608642578125, 3.547543525695801, 4.078277587890625, 5.6649675369262695, 21.502113342285156, 4.818630218505859, 3.028402090072632, 4.0498046875, 0.0, 2.7160840034484863, 5.697059154510498, 3.3423843383789062, 12.561591148376465, 4.248226165771484, 2.766164541244507, 4.936634540557861, 10.005887031555176, 9.519760131835938, 3.812408447265625, 7.6430816650390625, 2.6739463806152344, 3.4683380126953125, 3.3103349208831787, 24.305877685546875, 4.9918389320373535, 10.427536010742188, 7.62939453125e-06, 2.565502166748047, 7.297168254852295, 6.0010528564453125, 17.75743293762207, 13.325148582458496, 3.8234617710113525, 3.2093658447265625, 0.0, 0.0, 8.75095272064209, 4.011329650878906, 7.70086669921875, 15.42055892944336, 1.299192190170288, 2.904278516769409, 4.86720609664917, 1.9997299909591675, 20.32551383972168, 9.312362670898438, 9.244574546813965, 2.637341260910034, 3.833674907684326, 2.9508743286132812, 2.6190860271453857, 1.9787379503250122, 1.9366402626037598, 2.8805809020996094, 6.035037517547607, 3.869330883026123, 17.618492126464844, 3.87308931350708, 6.92744779586792, 8.392074584960938, 0.0, 1.5008468627929688, 5.642301082611084, 4.410869598388672, 13.350653648376465, 6.145820140838623, 4.224972724914551, 3.3244781494140625, 3.205974578857422, 2.973381519317627, 3.7568130493164062, 7.6429595947265625, 2.1901962757110596, 3.0788395404815674, 3.2181637287139893, 3.6313869953155518, 7.470557689666748, 28.675146102905273, 5.231986999511719, 5.462817192077637, 6.433250427246094, 7.545005798339844, 2.0067367553710938, 7.526546955108643, 4.134799480438232, 11.120689392089844, 2.0539052486419678, 5.079498291015625, 6.008067607879639, 2.3258414268493652, 14.379939079284668, 9.76413631439209, 3.835742712020874, 2.29769229888916, 5.893847465515137, 0.0, 10.641608238220215, 3.2211363315582275, 4.676994323730469, 4.452476501464844, 3.9566683769226074, 7.699653148651123, 2.961597442626953, 2.7936151027679443, 3.466801643371582, 10.725687980651855, 1.2390937805175781, 3.3199245929718018, 3.5563392639160156, 7.643869400024414, 1.5042511224746704, 9.570938110351562, 1.6144074201583862, 1.7162917852401733, 9.5367431640625e-07, 9.5367431640625e-07, 1.7358977794647217, 1.6640137434005737, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.4993716478347778, 1.5722243785858154, 9.5367431640625e-07, 1.968701720237732, 0.9628896713256836, 1.2872627973556519, 1.0141034126281738, 2.4798660278320312, 9.5367431640625e-07, 9.5367431640625e-07, 1.1109306812286377, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.1318387985229492, 1.4898334741592407, 1.2635271549224854, 9.5367431640625e-07, 9.5367431640625e-07, 1.1021357774734497, 9.5367431640625e-07, 9.5367431640625e-07, 2.110856533050537, 1.9891659021377563, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 1.3852300643920898, 1.8911064863204956, 1.787481665611267, 2.10939884185791, 9.5367431640625e-07, 9.5367431640625e-07, 1.7500410079956055, 9.5367431640625e-07, 1.3790464401245117, 1.3585320711135864, 9.5367431640625e-07, 1.479604959487915, 9.5367431640625e-07, 9.5367431640625e-07, 0.9637271165847778, 1.5182523727416992, 9.5367431640625e-07, 2.0005109310150146, 1.9137389659881592, 1.5396050214767456, 1.8793305158615112, 1.1596041917800903, 1.601930022239685, 0.9377755522727966, 9.5367431640625e-07, 1.6907992362976074, 1.410310983657837, 9.5367431640625e-07, 1.179677128791809, 1.1685891151428223, 9.5367431640625e-07, 9.5367431640625e-07, 1.5159215927124023, 1.4309279918670654, 1.6490628719329834, 1.8227509260177612, 0.9512662887573242, 1.0921854972839355, 1.5227404832839966, 1.6438299417495728, 0.8570374846458435, 1.4859777688980103, 1.7097272872924805, 9.5367431640625e-07, 1.4700067043304443, 1.5423650741577148, 1.1356916427612305, 9.5367431640625e-07, 1.4128566980361938, 0.9002065658569336, 0.0, 1.3455978631973267, 1.368538737297058, 9.5367431640625e-07, 1.0291218757629395, 1.501911997795105, 9.5367431640625e-07, 9.5367431640625e-07, 3.2674341201782227, 0.8605337142944336, 9.5367431640625e-07, 9.5367431640625e-07, 1.71097993850708, 9.5367431640625e-07, 9.5367431640625e-07, 1.5909919738769531, 0.7543506622314453, 0.32865434885025024, 1.560189127922058, 2.484617233276367, 0.8088731169700623, 9.5367431640625e-07, 0.45336249470710754, 9.5367431640625e-07, 1.913291573524475, 9.5367431640625e-07, 9.5367431640625e-07, 1.7397598028182983, 1.053871750831604, 9.5367431640625e-07, 1.3905858993530273, 1.1458250284194946, 9.5367431640625e-07, 1.1579935550689697, 1.653525471687317, 9.5367431640625e-07, 9.5367431640625e-07, 2.431128740310669, 9.5367431640625e-07, 1.1218384504318237, 9.5367431640625e-07, 1.1874855756759644, 1.2124637365341187, 9.5367431640625e-07, 9.5367431640625e-07, 1.0964384078979492, 2.383406639099121, 1.3662124872207642, 1.766457438468933, 1.6589783430099487, 9.5367431640625e-07, 9.5367431640625e-07, 1.174468994140625, 9.5367431640625e-07, 2.3884453773498535, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 1.6821355819702148, 9.5367431640625e-07, 2.938303232192993, 1.1822142601013184, 9.5367431640625e-07, 9.5367431640625e-07, 2.3435487747192383, 0.9446632266044617, 9.5367431640625e-07, 0.7279437184333801, 1.7316080331802368, 9.5367431640625e-07, 0.22104549407958984, 9.5367431640625e-07, 1.0160237550735474, 1.3045017719268799, 9.5367431640625e-07, 0.39145755767822266, 0.5818498730659485, 1.4523361921310425, 1.8036233186721802, 1.7205963134765625, 1.006205677986145, 0.962956964969635, 2.044644355773926, 1.8780802488327026, 1.3530797958374023, 1.078686237335205, 9.5367431640625e-07, 1.2885806560516357, 1.1515130996704102, 1.2478684186935425, 2.265014410018921, 1.5044463872909546, 9.5367431640625e-07, 2.2356479167938232, 1.2736748456954956, 1.5206327438354492, 1.9087181091308594, 9.5367431640625e-07, 2.6363186836242676, 9.5367431640625e-07, 1.5596368312835693, 9.5367431640625e-07, 1.0402202606201172, 0.2733621597290039, 1.8691062927246094, 9.5367431640625e-07, 9.5367431640625e-07, 1.073154330253601, 9.5367431640625e-07, 0.8891130089759827, 0.7786730527877808, 1.8519604206085205, 1.8059673309326172, 1.80515718460083, 2.2800228595733643, 9.5367431640625e-07, 2.668785572052002, 1.4452790021896362, 9.5367431640625e-07, 1.5153509378433228, 1.4913772344589233, 9.5367431640625e-07, 1.0065374374389648, 1.6335058212280273, 0.9223690032958984, 1.216180443763733, 1.6262872219085693, 1.5727638006210327, 9.5367431640625e-07, 1.2737066745758057, 0.7094335556030273, 0.8971145153045654, 1.2360904216766357, 1.7262039184570312, 1.5305849313735962, 1.8253835439682007, 1.3685075044631958, 9.5367431640625e-07, 0.8471049070358276, 1.00865638256073, 2.2393972873687744, 1.3337715864181519, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.1023681163787842, 1.4458969831466675, 0.44024181365966797, 9.5367431640625e-07, 9.5367431640625e-07, 0.5816888809204102, 0.9290326237678528, 0.18726444244384766, 1.501960277557373, 9.5367431640625e-07, 1.7278565168380737, 1.230687141418457, 1.5388517379760742, 1.2716283798217773, 2.063206672668457, 9.5367431640625e-07, 1.1086831092834473, 1.381255030632019, 9.5367431640625e-07, 1.5048571825027466, 0.943192720413208, 1.4319961071014404, 9.5367431640625e-07, 9.5367431640625e-07, 1.8548461198806763, 0.9715631008148193, 9.5367431640625e-07, 0.0, 1.0768173933029175, 9.5367431640625e-07, 1.3183050155639648, 1.427876353263855, 0.891140878200531, 9.5367431640625e-07, 2.300499677658081, 1.059401512145996, 1.048426628112793, 1.6462514400482178, 9.5367431640625e-07, 2.1450536251068115, 9.5367431640625e-07, 9.5367431640625e-07, 1.1561940908432007, 1.2330559492111206, 2.110628604888916, 1.8321621417999268, 9.5367431640625e-07, 0.9855462312698364, 1.8038134574890137, 1.5045706033706665, 2.3326261043548584, 9.5367431640625e-07, 1.4717117547988892, 9.5367431640625e-07, 1.6153810024261475, 1.497973084449768, 1.2638639211654663, 9.5367431640625e-07, 1.934828758239746, 9.5367431640625e-07, 1.2642896175384521, 9.5367431640625e-07, 1.7552876472473145, 9.5367431640625e-07, 9.5367431640625e-07, 1.9829692840576172, 0.0, 0.0, 0.082432322204113, 0.01624254323542118, 0.0, 0.0, 0.006175023037940264, 0.0, 0.0, 0.0708322525024414, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0023418408818542957, 0.029561582952737808, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0005006819847039878, 2.843916263373103e-05, 4.063189044245519e-05, 0.0, 0.0, 0.005715554114431143, 0.0, 0.0, 0.009229215793311596, 0.0, 1.19209286886246e-09, 0.01034221425652504, 0.02505575679242611, 0.0, 0.0, 0.004915708210319281, 0.0, 0.0, 1.5497207641601562e-06, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 4.172325134277344e-07, 5.9604643443123e-10, 0.0, 0.0, 0.0, 0.024864988401532173, 0.0, 0.0, 0.0002761274517979473, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.38418573772492e-09, 0.0, 0.0, 0.0, 0.0003108101955149323, 0.017879558727145195, 0.0, 0.02113187313079834, 0.001097261905670166, 0.0, 0.0, 0.026480387896299362, 0.0, 0.0, 5.960464477539063e-08, 1.6933679489739006e-06, 0.0, 0.006300967652350664, 0.0, 0.0, 0.0, 0.01752406358718872, 0.012260088697075844, 0.0, 0.003166009671986103, 0.0045080934651196, 0.0, 0.006897101644426584, 0.003629047889262438, 0.0, 2.379179022682365e-05, 0.0, 0.0005734598380513489, 0.0, 8.037149382289499e-05, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.19209286886246e-09, 0.0390261746942997, 0.0, 0.0021992360707372427, 0.0, 0.007527172565460205, 0.0, 1.7881393032936899e-09, 0.001045013079419732, 0.00784158706665039, 0.0021578073501586914, 0.0, 0.0, 0.0, 0.02116573601961136, 0.0, 0.0, 0.0, 0.0, 4.172325134277344e-06, 1.7881393032936899e-09, 0.0012069379445165396, 2.923905776697211e-05, 8.603811147622764e-05, 0.0, 0.0, 0.023305615410208702, 0.0, 9.49621153267799e-06, 0.0, 0.004746794700622559, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.03281655162572861, 0.0004370403185021132, 0.0, 7.050036947475746e-05, 0.0, 0.0, 0.0, 0.0, 0.0009909272193908691, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0013383745681494474, 0.0, 0.020744284614920616, 5.914389839745127e-05, 0.0014981627464294434, 5.125999450683594e-06, 0.0, 3.5762786865234375e-07, 0.0013398956507444382, 0.0032117366790771484, 0.0, 0.0, 0.0027827697340399027, 0.0, 0.0, 0.0, 0.002571334131062031, 0.0, 3.0101537049631588e-05, 0.0, 0.0, 0.023171450942754745, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0005608219071291387, 0.0, 0.002150102751329541, 0.0, 0.0, 0.0, 0.0, 2.7418135317702763e-08, 0.01564481481909752, 0.0024059456773102283, 0.0, 0.00824115052819252, 0.0, 0.0, 0.03573856130242348, 0.0, 5.9604643443123e-10, 0.002582178683951497, 0.0, 0.022537020966410637, 0.0, 0.0, 0.0, 0.0, 0.00014454186020884663, 0.0, 7.98940618551569e-06, 0.0037391185760498047, 0.0060921586118638515, 5.9604643443123e-10, 0.006433235481381416, 0.00015109717787709087, 0.0, 0.00894765555858612, 0.0, 0.0, 0.0, 0.0, 5.9604643443123e-10, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.3514032818638952e-06, 5.599260020971997e-06, 7.155775529099628e-05, 0.0, 0.0, 0.0, 0.0, 0.0, 0.003839076729491353, 0.0, 1.7881393032936899e-09, 0.0, 0.0, 0.09859436750411987, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.7881393032936899e-09, 0.0, 8.286833690362982e-06, 0.0, 0.004221278242766857, 0.0, 0.0, 0.0, 0.0, 0.05978813022375107, 0.0, 5.9604643443123e-10, 0.0, 0.0, 0.006901990156620741, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0017056041397154331, 0.0, 0.0, 0.0, 0.0, 0.000979193369857967, 9.62614990385191e-07, 5.9604643443123e-10, 0.011959799565374851, 0.0, 0.016806142404675484, 0.010899127461016178, 0.0, 0.002618372905999422, 0.0, 0.0, 0.0, 0.0, 0.0, 3.826618194580078e-05, 0.10268685966730118, 8.601655154751205e-15, 1.3079428761841178e-14, 1.3798375927910524e-14, 1.0118996095144668e-14, 5.367629999058609e-15, 7.397538527922909e-15, 6.1949935707282435e-15, 5.8029625822999566e-15, 8.304355060594418e-15, 0.0940774530172348, 8.797383293037992e-15, 4.446263134419166e-15, 0.02330540306866169, 1.3309194919113379e-14, 1.0402581031819513e-14, 9.003231780978574e-15, 0.0507500059902668, 0.1888153851032257, 1.1491631620895101e-14, 0.09392980486154556, 1.2560575341868767e-14, 0.11556676775217056, 1.0331648798750544e-14, 0.22172890603542328, 0.11260578036308289, 1.1294216192977383e-14, 0.09590156376361847, 0.02472829259932041, 1.1973431584589873e-14, 0.11771859973669052, 1.0257686728829245e-14, 0.10605897754430771, 0.001666676951572299, 0.08685405552387238, 4.709655229147942e-15, 0.20910926163196564, 1.1167820242522202e-14, 0.09450504928827286, 7.265556395180586e-15, 9.985395282440142e-15, 0.0877903550863266, 0.09520967304706573, 3.987132313491761e-15, 6.952905099404235e-15, 0.11124982684850693, 0.21880391240119934, 0.2150711566209793, 8.932203833186565e-15, 0.09251029789447784, 3.935437892720831e-15, 0.12422958761453629, 0.013737725093960762, 1.2223477404685237e-14, 1.0631010571100948e-14, 1.4057158045823869e-14, 0.017833668738603592, 6.329457086489548e-15, 6.858903500500321e-15, 0.10517850518226624, 9.025972394738346e-05, 0.09777774661779404, 0.23309223353862762, 0.09907623380422592, 1.382929771268299e-14, 1.470919130312602e-14, 0.09946242719888687, 0.07505063712596893, 0.11674026399850845, 8.380436406949746e-15, 1.4773287980310648e-14, 0.09142709523439407, 1.500030805676785e-14, 0.008137148804962635, 0.10552085936069489, 7.920913409767763e-15, 0.22754745185375214, 0.17553237080574036, 8.615710819477942e-15, 1.0112082612229178e-14, 4.08600350480944e-15, 7.316032782573364e-15, 0.20601852238178253, 0.11276742815971375, 0.003125465475022793, 5.131137976668735e-15, 8.008444100471128e-15, 1.1843440826306544e-14, 0.0001944724062923342, 0.19174468517303467, 0.11163382977247238, 0.10943128168582916, 8.801971670513269e-15, 4.0668122793234996e-15, 0.2180657535791397, 0.007311592344194651, 4.930425473003829e-15, 4.934132936213961e-15, 8.261435901157042e-15, 0.0924694836139679, 0.08114013820886612, 1.3747674229753776e-14, 0.1875062733888626, 1.0582893170466273e-14, 0.07504205405712128, 0.09742861241102219, 1.1588518637533837e-14, 1.4798375402142426e-14, 1.1709631643496993e-14, 1.0643543270588522e-14, 0.21448341012001038, 9.643230394166136e-15, 1.2574016907708745e-14, 1.4733850126286488e-14, 0.09386750310659409, 0.0167243592441082, 1.3837185283487822e-14, 0.22143326699733734, 0.1096290573477745, 9.323788011735175e-15, 1.2185644678096123e-14, 9.052374938512374e-15, 0.14027312397956848, 0.004857190884649754, 8.001454384590385e-15, 1.0686033831354587e-14, 0.06867589801549911, 0.001010783831588924, 1.2534978006202742e-14, 0.10414443910121918, 1.4351152170387522e-14, 8.052125589561032e-15, 0.31604909896850586, 0.1034536138176918, 1.3698966447154865e-14, 1.2141637081321526e-14, 0.08395256102085114, 9.338608547213283e-15, 1.1440521652857777e-14, 0.0878109559416771, 0.0017368417466059327, 0.009905585087835789, 7.8755226081903e-15, 0.03631078824400902, 8.979008332752995e-15, 8.347206457396013e-15, 0.1019064337015152, 0.11052152514457703, 9.503119286229014e-15, 1.1978675565566324e-14, 1.1694546833739342e-14, 6.026810943886166e-15, 0.06190496310591698, 0.10198042541742325, 0.11839696019887924, 0.00041271309601143, 8.17753220553382e-15, 0.007631647866219282, 1.1180494396511968e-14, 0.10513995587825775, 0.11864801496267319, 5.325893721132074e-15, 1.1157574531992214e-14, 0.22846093773841858, 0.09604305028915405, 0.20029929280281067, 1.0047337954839902e-14, 0.1181035190820694, 1.394051313865748e-14, 0.011927993968129158, 0.0928758755326271, 0.0793396532535553, 0.11275670677423477, 0.05003124102950096, 0.09239019453525543, 9.617870227725343e-15, 4.072187550406775e-15, 5.833213093461723e-15, 0.11028270423412323, 0.11780544370412827, 0.09546991437673569, 0.10826908051967621, 9.39937977304699e-15, 0.11644808202981949, 9.339851144546905e-15, 0.07684596627950668, 4.1965446925579155e-15, 0.1185290589928627, 1.401665547138501e-14, 0.2186080515384674, 0.09825581312179565, 0.09499815851449966, 1.0369066479195502e-14, 1.469660778166161e-14, 1.4787599448987457e-14, 0.00019920736667700112, 4.440953931905776e-15, 0.09066442400217056, 3.949134838994407e-15, 9.225315349419179e-15, 6.793678998946425e-15, 0.012117412872612476, 1.438877059764098e-14, 1.0423532391769848e-14, 6.1482165997325984e-15, 0.20666198432445526, 0.09881874173879623, 1.0125069321376481e-14, 0.2306784838438034, 4.429200502729675e-15, 0.10155828297138214, 0.09924907237291336, 0.016463356092572212, 1.5104670986199054e-14, 1.1915192140235509e-14, 0.13608025014400482, 0.009010798297822475, 0.023444589227437973, 0.08533988893032074, 8.028797455160702e-15, 0.05037648230791092, 0.1044866219162941, 4.1682156756369954e-15, 1.0286428250795478e-14, 0.11652064323425293, 0.18080392479896545, 0.022546717897057533, 1.1293074392564485e-14, 0.08054852485656738, 0.006589279044419527, 0.12361633032560349, 1.1667345217671217e-14, 0.15006354451179504, 0.09677740186452866, 1.0634452912998589e-14, 1.3492158270885044e-14, 0.10990763455629349, 0.07923576980829239, 0.08649005740880966, 0.07428538799285889, 0.22772425413131714, 0.0030714247841387987, 0.22836968302726746, 1.4183784389240704e-14, 1.0001567682502068e-14, 5.128708686176009e-15, 7.810789809262284e-15, 1.2110687344461801e-14, 0.005193048156797886, 0.0002413780166534707, 0.13316555321216583, 1.1942685982670436e-14, 6.0248225340424864e-15, 0.0884789451956749, 6.273359364942317e-15, 0.07320243865251541, 0.21531903743743896, 0.11728264391422272, 0.09604287147521973, 0.11574476957321167, 4.7288773713364575e-15, 1.4703582250949303e-14, 1.2701076931994574e-14, 0.11365088820457458, 0.10518680512905121, 0.11346641927957535, 0.004902799613773823, 0.014657373540103436, 1.353644708259813e-14, 4.3523864728749716e-15, 0.019162548705935478, 6.875968673288654e-15, 5.6239146403269744e-15, 6.310849043187792e-15, 0.09550837427377701, 0.0025765288155525923, 7.323255432514601e-15, 0.1111190989613533, 5.120217180879785e-15, 1.3764187984093446e-14, 9.528028831141868e-15, 0.10722524672746658, 6.000563510433123e-15, 1.1914446751241925e-14, 0.10977569967508316, 9.932868228282061e-15, 1.1481013215868321e-14, 0.10647586733102798, 0.11385609209537506, 0.09570222347974777, 0.09920892864465714, 0.11230449378490448, 6.321948139412139e-15, 7.174193727423842e-15, 0.09158758074045181, 0.11271730065345764, 6.8345555384314964e-15, 0.11663385480642319, 0.11028297245502472, 0.11186381429433823, 1.9844433069229126, 2.9037201404571533, 2.747912645339966, 3.231950283050537, 3.5348129272460938, 4.638969421386719, 15.075201988220215, 9.75212287902832, 8.831936836242676, 0.0, 1.9937258958816528, 4.231101989746094, 4.073490142822266, 3.749420166015625, 9.99848747253418, 5.833998680114746, 5.337344646453857, 4.928738594055176, 3.5540695190429688, 4.986044406890869, 5.78948974609375, 7.561194896697998, 8.752264976501465, 4.7588725090026855, 6.205605506896973, 3.4565069675445557, 5.105476379394531, 4.246734619140625, 1.4816902875900269, 11.484542846679688, 16.98712158203125, 7.137474060058594, 3.2203752994537354, 13.32607364654541, 5.123435974121094, 3.5046539306640625, 2.7782864570617676, 5.987968444824219, 5.959573745727539, 5.6378631591796875, 4.443164348602295, 5.456635475158691, 3.096775770187378, 7.488724708557129, 2.601841926574707, 7.039852142333984, 0.0077667236328125, 3.462559461593628, 3.9938879013061523, 15.86214828491211, 5.2957000732421875, 6.646417140960693, 4.868463516235352, 3.6367530822753906, 6.576019287109375, 3.720400333404541, 3.589398145675659, 4.076193809509277, 10.085891723632812, 0.0, 2.282609701156616, 4.555278778076172, 3.1831278800964355, 7.067604064941406, 8.680953979492188, 7.3154191970825195, 7.266227722167969, 38.47386169433594, 2.4717330932617188, 2.0122878551483154, 9.176140785217285, 3.429473876953125, 8.759300231933594, 6.534703254699707, 4.759620666503906, 4.766197204589844, 0.0, 5.981447696685791, 10.538226127624512, 6.204334735870361, 3.1660385131835938, 4.755645751953125, 4.191795349121094, 3.134366989135742, 10.370624542236328, 4.642757892608643, 2.907817840576172, 2.623189926147461, 9.02599048614502, 6.26035737991333, 7.622565746307373, 4.029155731201172, 6.914897441864014, 5.20207405090332, 9.562314987182617, 1.0066337585449219, 12.535942077636719, 4.5714030265808105, 0.0, 3.0619311332702637, 7.950523376464844, 5.087352752685547, 6.823326110839844, 9.616156578063965, 3.0414657592773438, 0.0, 20.088851928710938, 2.89093017578125, 2.629956007003784, 3.6798477172851562, 4.377467155456543, 12.230897903442383, 1.008697509765625, 0.0, 1.7947769165039062, 1.9594035148620605, 7.508674144744873, 0.0, 4.43166971206665, 2.420604705810547, 11.893075942993164, 22.244613647460938, 4.92210578918457, 0.0, 2.9551773071289062, 7.3341522216796875, 17.20856475830078, 12.296576499938965, 7.55255126953125, 8.089523315429688, 2.007222890853882, 3.0163772106170654, 16.768619537353516, 5.0107879638671875, 11.577545166015625, 5.979529857635498, 25.00751495361328, 2.7716751098632812, 6.728309154510498, 5.562201976776123, 3.344965696334839, 3.227741003036499, 24.702743530273438, 14.095611572265625, 5.9193291664123535, 6.029386043548584, 1.991536259651184, 5.736480712890625, 16.16592025756836, 6.157604217529297, 3.5363845825195312, 7.9757537841796875, 4.130565643310547, 3.6462860107421875, 4.83984899520874, 20.05621337890625, 4.9425435066223145, 11.950249671936035, 8.351768493652344, 10.12508487701416, 10.867349624633789, 10.660284996032715, 3.390010356903076, 12.378424644470215, 2.8295440673828125, 3.3003268241882324, 8.861106872558594, 2.9385435581207275, 7.740456581115723, 3.3989007472991943, 3.981457233428955, 17.610870361328125, 10.12493896484375, 3.1198196411132812, 7.401420593261719, 3.840123176574707, 9.066575050354004, 6.936925411224365, 23.75690460205078, 3.8848214149475098, 8.683938026428223, 0.0, 3.253898859024048, 5.7440924644470215, 7.1930389404296875, 10.28738021850586, 4.192902088165283, 4.555052280426025, 5.561153411865234, 3.681405782699585, 1.9584072828292847, 20.402151107788086, 4.3492889404296875, 5.094635009765625, 6.765510082244873, 5.067779541015625, 4.470985412597656, 3.863957643508911, 4.27554178237915, 4.512991905212402, 2.095733642578125, 3.2790298461914062, 5.582204341888428, 3.25179123878479, 21.28045654296875, 5.220234394073486, 3.9349334239959717, 0.0, 8.383435249328613, 7.770477294921875, 8.377860069274902, 3.5753250122070312, 14.611090660095215, 22.038930892944336, 2.6839306354522705, 3.5068838596343994, 11.926200866699219, 6.45849609375, 2.0118093490600586, 9.76375675201416, 6.708854675292969, 2.5070388317108154, 4.126430511474609, 4.129909515380859, 2.324920892715454, 9.024406433105469, 23.038177490234375, 4.716160774230957, 2.081317663192749, 5.092921257019043, 4.084266662597656, 9.224030494689941, 3.835686445236206, 3.3193166255950928, 2.9520113468170166, 3.8115508556365967, 7.920249938964844, 6.0697832107543945, 28.96441650390625, 12.655937194824219, 12.892279624938965, 3.8949334621429443, 3.0750198364257812, 15.982757568359375, 4.374176025390625, 10.2315034866333, 19.72404670715332, 2.701556921005249, 3.881619691848755, 5.913738250732422, 4.8263630867004395, 19.226694107055664, 7.469227313995361, 1.366707682609558, 8.53696346282959, 7.78505277633667, 4.484619140625, 3.5301449298858643, 7.121420860290527, 4.459352016448975, 24.787748336791992, 9.648475646972656, 2.8126561641693115, 15.461906433105469, 11.4183349609375, 4.498696327209473, 2.2265405654907227, 8.211129188537598, 6.1533050537109375, 2.221550464630127, 2.676872491836548, 7.040876865386963, 9.325885772705078, 4.584266185760498, 0.0, 3.9188385009765625, 5.386713981628418, 4.06478214263916, 4.969205379486084, 1.9228439331054688, 4.770442962646484, 3.8783328533172607, 5.6354875564575195, 7.193265438079834, 4.1380767822265625, 2.991614818572998, 5.365058422088623, 3.2565243244171143, 5.120944499969482, 13.1708984375, 16.34117889404297, 3.3122622966766357, 12.11091423034668, 2.397174835205078, 9.691400527954102, 7.411094665527344, 2.345916748046875, 3.5550155639648438, 4.007627010345459, 3.307013511657715, 1.0000487565994263, 1.4612035751342773, 9.5367431640625e-07, 1.814534068107605, 1.4969402551651, 2.8843939304351807, 1.7464475631713867, 9.5367431640625e-07, 1.1407701969146729, 9.5367431640625e-07, 2.288874387741089, 1.117761254310608, 1.4806817770004272, 1.6073205471038818, 1.1921969652175903, 1.220052719116211, 1.2041820287704468, 1.4178217649459839, 0.6079568862915039, 1.7580808401107788, 1.7055481672286987, 9.5367431640625e-07, 0.8255425691604614, 1.6937493085861206, 9.5367431640625e-07, 1.7574248313903809, 1.9972631931304932, 0.9147359132766724, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.3889350891113281, 9.5367431640625e-07, 1.4277195930480957, 2.100658416748047, 1.1871501207351685, 1.888031244277954, 1.7791802883148193, 1.4267315864562988, 1.370613932609558, 0.30341148376464844, 2.0935263633728027, 1.2957741022109985, 1.112655520439148, 1.1379104852676392, 1.3715264797210693, 1.4438903331756592, 0.8594748377799988, 9.5367431640625e-07, 1.329433560371399, 2.3117997646331787, 1.3794606924057007, 1.1781185865402222, 2.1232333183288574, 9.5367431640625e-07, 2.163581609725952, 0.35300350189208984, 9.5367431640625e-07, 1.0330551862716675, 9.5367431640625e-07, 0.3183622360229492, 9.5367431640625e-07, 0.013919029384851456, 9.5367431640625e-07, 1.527840495109558, 9.5367431640625e-07, 1.2364352941513062, 0.37496161460876465, 1.744702696800232, 1.4005765914916992, 9.5367431640625e-07, 1.1897629499435425, 1.240166425704956, 0.8537389039993286, 2.3338022232055664, 1.7400907278060913, 1.347145915031433, 1.7455520629882812, 1.2623287439346313, 9.5367431640625e-07, 1.5036019086837769, 2.2914137840270996, 2.2533199787139893, 2.092404365539551, 1.6117464303970337, 1.3803986310958862, 9.5367431640625e-07, 9.5367431640625e-07, 1.7928109169006348, 1.8519471883773804, 1.853562831878662, 1.224242925643921, 1.8507894277572632, 0.8655663728713989, 2.0900816917419434, 1.701655387878418, 1.4511687755584717, 9.5367431640625e-07, 0.0, 9.5367431640625e-07, 0.9071455001831055, 1.3061976432800293, 9.5367431640625e-07, 1.7382917404174805, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.8873116970062256, 2.770768404006958, 0.9646081328392029, 2.405209541320801, 2.0115842819213867, 1.4561611413955688, 2.109219551086426, 1.177937626838684, 0.41263389587402344, 2.3295462131500244, 9.5367431640625e-07, 9.5367431640625e-07, 1.5321356058120728, 0.9367898106575012, 2.0079565048217773, 9.5367431640625e-07, 1.4094805717468262, 9.5367431640625e-07, 1.2659833431243896, 1.1835637092590332, 9.5367431640625e-07, 9.5367431640625e-07, 1.3837413787841797, 0.2294321060180664, 9.5367431640625e-07, 9.5367431640625e-07, 0.8551464080810547, 1.342477560043335, 9.5367431640625e-07, 1.8954311609268188, 0.1052713394165039, 0.8892373442649841, 1.5184165239334106, 1.6975491046905518, 0.3340177536010742, 2.140599250793457, 1.4792946577072144, 9.5367431640625e-07, 9.5367431640625e-07, 1.7679985761642456, 0.6481199264526367, 9.5367431640625e-07, 1.4545491933822632, 9.5367431640625e-07, 9.5367431640625e-07, 0.8180937767028809, 1.8683193922042847, 1.5207061767578125, 9.5367431640625e-07, 9.5367431640625e-07, 1.538621187210083, 1.1301908493041992, 1.4976030588150024, 1.1004180908203125, 1.1890909671783447, 1.6804876327514648, 0.06684017181396484, 1.9068732261657715, 2.2264671325683594, 1.0293151140213013, 1.5523709058761597, 1.3600510358810425, 1.7553129196166992, 1.4030381441116333, 9.5367431640625e-07, 9.5367431640625e-07, 1.687641978263855, 1.2909117937088013, 1.6054638624191284, 9.5367431640625e-07, 0.7933149337768555, 1.4728367328643799, 1.5110359191894531, 9.5367431640625e-07, 9.5367431640625e-07, 1.3154267072677612, 1.374052882194519, 0.018097877502441406, 1.5327775478363037, 9.5367431640625e-07, 1.0795029401779175, 0.944330096244812, 0.9552621245384216, 9.5367431640625e-07, 0.8576974272727966, 1.4138989448547363, 1.6982336044311523, 2.502775192260742, 0.8924650549888611, 1.6393483877182007, 1.898457407951355, 1.3861855268478394, 9.5367431640625e-07, 0.5723341107368469, 0.5179414749145508, 1.033445119857788, 1.3898752927780151, 0.052605628967285156, 9.5367431640625e-07, 0.6659727096557617, 1.587598204612732, 1.684960126876831, 9.5367431640625e-07, 9.5367431640625e-07, 1.4828835725784302, 1.7281774282455444, 2.197937250137329, 0.7213611602783203, 2.0010805130004883, 1.5182485580444336, 1.7643009424209595, 1.9215096235275269, 1.4695615768432617, 1.286843180656433, 0.11730098724365234, 1.15471613407135, 9.5367431640625e-07, 1.244693398475647, 9.5367431640625e-07, 1.4163826704025269, 1.8025046586990356, 2.52616810798645, 1.7589296102523804, 0.660856306552887, 1.632943034172058, 1.6878312826156616, 1.3111076354980469, 9.5367431640625e-07, 1.1498011350631714, 1.0138283967971802, 0.9450578093528748, 9.5367431640625e-07, 0.8817307949066162, 9.5367431640625e-07, 1.5352425575256348, 0.7890712022781372, 1.4975080490112305, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 2.530492067337036, 9.5367431640625e-07, 9.5367431640625e-07, 0.8835201859474182, 9.5367431640625e-07, 1.2710142135620117, 9.5367431640625e-07, 2.270808219909668, 1.5900754928588867, 2.0486066341400146, 2.9267146587371826, 1.22386634349823, 0.9282884001731873, 2.015307664871216, 1.0306355953216553, 9.5367431640625e-07, 9.5367431640625e-07, 1.3471670150756836, 1.034194827079773, 1.5469890832901, 9.5367431640625e-07, 1.386012077331543, 2.4943490028381348, 1.413485050201416, 1.552940845489502, 0.9419715404510498, 1.5393636226654053, 1.8461096286773682, 1.3858333826065063, 1.001895546913147, 1.6746625900268555, 1.3268842697143555, 1.3250257968902588, 1.3239716291427612, 1.1875988245010376, 0.770237386226654, 1.3932323455810547, 1.8151460886001587, 0.9037838578224182, 1.6754648685455322, 1.1911752223968506, 1.0318230390548706, 9.5367431640625e-07, 9.5367431640625e-07, 1.34870445728302, 1.2365883588790894, 1.4305181503295898, 1.8267000913619995, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 1.884934663772583, 1.9008703231811523, 0.0, 0.0, 0.0, 0.0, 2.7083753593615256e-05, 0.0, 0.011372703127563, 0.0, 0.0, 0.0, 5.9604643443123e-10, 0.0, 0.0, 1.722574234008789e-05, 0.002971191890537739, 0.00016975283506326377, 0.003299487056210637, 0.00025534629821777344, 0.002690497087314725, 0.0, 1.3293027222971432e-05, 0.0, 0.0, 0.0, 0.0, 4.172325152040912e-09, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.9802322387695312e-08, 0.00012831270578317344, 0.0, 0.009701911360025406, 0.0, 0.004572961945086718, 0.0, 0.0002607399073895067, 0.001964212628081441, 0.005348899867385626, 0.013954667374491692, 0.0, 0.0032661978621035814, 0.027598289772868156, 0.0, 0.0, 0.0, 0.0, 0.0, 0.02177824266254902, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.019844593480229378, 0.0, 0.03198057413101196, 0.0, 0.006357252597808838, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.012005929835140705, 0.011085009202361107, 0.0, 0.0, 0.0, 0.0, 0.0, 0.00304444064386189, 0.0, 0.008228244259953499, 0.0, 0.0, 0.002876046346500516, 0.0, 0.007580220699310303, 0.012211767956614494, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0002798443892970681, 0.0, 0.0, 0.0, 0.0, 0.0, 0.016377270221710205, 0.0, 0.0, 0.0010904669761657715, 0.0, 3.7785768654430285e-05, 0.0, 0.0, 0.0, 0.0, 1.19209286886246e-09, 0.0037094098515808582, 0.0019222503760829568, 0.010376514866948128, 0.00018237710173707455, 0.0, 0.0, 0.0, 0.0, 0.0, 0.00010609686432871968, 0.022956091910600662, 0.0, 1.7881392366803084e-08, 0.04105854034423828, 0.02775493822991848, 0.00028842687606811523, 2.550542376411613e-05, 0.062101658433675766, 0.0, 0.001313046202994883, 0.0, 2.0210742150084116e-05, 0.004492342472076416, 0.0005046164733357728, 0.0, 0.0, 5.543232006743892e-08, 0.03913584724068642, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0016859173774719238, 0.0, 0.0, 0.0, 1.19209286886246e-09, 0.0, 0.0, 0.001535580726340413, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0011203241301700473, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.009141683578491211, 1.4963149624236394e-05, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.04879291355609894, 0.0008206963539123535, 0.00020509480964392424, 0.0017802673391997814, 0.0, 0.0, 0.05805271863937378, 0.00015937745047267526, 0.008527643047273159, 0.0, 0.002115539973601699, 0.0, 0.08721800893545151, 0.0, 0.00047722578165121377, 0.0, 0.0014543711440637708, 0.018649041652679443, 0.0, 0.0005250722169876099, 0.009202361106872559, 0.0, 0.0, 0.00031394363031722605, 0.030591489747166634, 0.0, 0.004039224702864885, 0.0, 0.0007411569240503013, 0.0003348517348058522, 0.0, 0.0, 0.03628586605191231, 0.0, 0.0, 0.0, 0.020630788058042526, 0.01474262960255146, 0.0, 0.0, 0.002047501737251878, 0.0, 0.0, 0.0, 2.7948617571382783e-06, 0.0013582706451416016, 0.0, 0.00842750072479248, 0.0, 0.0, 0.0, 0.02061779424548149, 0.018848786130547523, 5.793571472167969e-05, 0.03733682632446289, 0.0, 0.01722661405801773, 0.0, 2.1457672119140625e-06, 0.011957662180066109, 0.00039894282235763967, 0.0, 0.01586555503308773, 0.082432322204113, 0.0, 0.0, 0.0, 0.0, 0.0708322525024414, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.006898939609527588, 0.002049531787633896, 0.0, 0.0, 0.0, 0.0, 0.013776796869933605, 0.0003052359679713845, 0.0, 0.05529302358627319, 0.00030198812601156533, 0.0051247188821434975, 0.0, 0.0, 0.0, 0.004721407312899828, 6.704330189677421e-06, 5.841254946403751e-08, 0.017441285774111748, 0.0, 0.0, 0.00861795898526907, 0.0, 0.03298420459032059, 0.0, 0.00040389536297880113, 0.0, 0.0, 0.0008123701554723084, 0.0, 0.0010264002485200763, 5.567669722950086e-05, 0.0, 1.19209286886246e-09, 0.01548740454018116, 0.0, 0.01894497312605381, 5.018114734411938e-06, 0.0, 0.00019663572311401367, 0.012709827162325382, 0.0, 0.008341150358319283, 0.0, 0.0, 8.653171698603211e-15, 8.363915876346498e-15, 0.00013230839977040887, 0.013178497552871704, 0.1879280060529709, 0.08489872515201569, 0.10103759169578552, 1.1629358331085703e-14, 0.229326531291008, 0.1451692432165146, 0.13092727959156036, 0.0998038649559021, 0.18698237836360931, 0.22663229703903198, 0.09694083780050278, 0.21428819000720978, 4.126251545847649e-15, 1.2506330504893654e-14, 0.10473986715078354, 0.0004339072620496154, 4.550242357925262e-15, 7.456617381928002e-15, 0.09849081188440323, 0.0029733970295637846, 6.603626828439188e-15, 4.3116285180025155e-15, 0.08893276005983353, 1.4383109029421533e-14, 0.11565349996089935, 1.3442599220174142e-14, 7.354946323203174e-15, 0.10212360322475433, 0.06355299055576324, 6.178704280119596e-15, 1.0164663876495884e-14, 8.941860855818211e-15, 8.733520396946807e-15, 0.10050947964191437, 6.898392176501317e-15, 0.0029566653538495302, 8.79299735643711e-15, 0.10130774974822998, 4.670697219288401e-15, 0.102198027074337, 0.1027371883392334, 5.83533194637928e-15, 4.0896529462626854e-15, 1.422053968992091e-14, 0.11411422491073608, 0.08135370910167694, 1.5049220821339998e-14, 0.1172289252281189, 7.360653631201773e-15, 0.11914946883916855, 1.428752644352157e-14, 1.085921225851957e-14, 0.09821378439664841, 8.675147121386777e-15, 0.1147700846195221, 0.10210150480270386, 0.10145215690135956, 0.1423550546169281, 0.006009557284414768, 0.08161614090204239, 0.09429529309272766, 6.529218795671161e-15, 0.11504314094781876, 9.599857225069033e-15, 0.025727903470396996, 0.08803649991750717, 5.71190315233833e-15, 0.09902238845825195, 7.359401716505731e-15, 0.08053521811962128, 0.11493314802646637, 0.2061830312013626, 0.12335806339979172, 0.20125539600849152, 0.09051535278558731, 0.09137889742851257, 0.11809959262609482, 0.1099107563495636, 1.2680040021716566e-14, 0.034230172634124756, 0.10049304366111755, 0.10230914503335953, 0.00026482250541448593, 9.53250455323516e-15, 1.1816256150897365e-14, 0.09400037676095963, 0.11799744516611099, 0.08006797730922699, 9.543037407934267e-15, 0.20797747373580933, 0.10722477734088898, 0.08344193547964096, 0.09163586050271988, 0.009771905839443207, 0.09832870215177536, 0.07735202461481094, 0.08785773813724518, 0.22043700516223907, 0.08617601543664932, 0.08346478641033173, 0.10801032930612564, 0.00016917444008868188, 9.3414105322028e-15, 3.903066834575614e-15, 1.4571971965670824e-14, 0.11948934942483902, 0.11120614409446716, 0.09267299622297287, 0.10593999922275543, 0.0054642860777676105, 0.10919111967086792, 1.1867891279361987e-14, 0.200431227684021, 0.0007265604799613357, 0.11391250044107437, 0.1994445025920868, 9.26918911498811e-15, 0.09919712692499161, 1.3542480498281422e-14, 6.932220554832285e-15, 8.492501406970332e-15, 1.485881120292902e-14, 4.860485962549042e-15, 1.0455225823557263e-14, 0.11036091297864914, 0.00011574329255381599, 0.09918670356273651, 1.0129489986328202e-14, 0.08844224363565445, 0.10539432615041733, 0.06339023262262344, 1.058290333486164e-14, 1.2183515237266726e-14, 1.3742381120866384e-14, 0.06288251280784607, 3.737027509487234e-05, 0.08245696127414703, 0.09550658613443375, 0.09479228407144547, 1.4400793383294308e-14, 0.10152524709701538, 0.11474422365427017, 5.692687786413393e-15, 0.09980820119380951, 0.20498424768447876, 1.3035477069241099e-14, 8.090858712173077e-15, 0.08805837482213974, 0.11892155557870865, 0.09885366261005402, 4.116344648496563e-15, 9.167325779784255e-15, 0.09317728132009506, 0.05536011606454849, 0.09376517683267593, 5.918206496971588e-15, 0.013082725927233696, 0.10150495916604996, 9.94099720347686e-15, 0.11808308959007263, 0.11241708695888519, 0.22780105471611023, 7.184380145647522e-15, 8.249130206499332e-15, 0.2004891186952591, 0.2095736712217331, 0.0843355730175972, 0.04616742953658104, 1.4794738242666916e-14, 1.489733595543604e-14, 0.0003831360081676394, 1.1803539645260236e-14, 0.11165180057287216, 9.291549937762676e-15, 9.79821709472294e-15, 9.336318170123908e-15, 0.1173558384180069, 1.0902144970484102e-14, 1.0585327543156681e-14, 0.11510492861270905, 0.21828097105026245, 8.336927712581082e-15, 0.10330218076705933, 0.010606305673718452, 8.622946174913389e-15, 1.262392070082918e-14, 1.422351616369756e-14, 9.418322817879386e-15, 1.2339925800207863e-14, 9.823316375015979e-15, 1.4858186092613947e-14, 0.14595754444599152, 0.11731061339378357, 0.12830089032649994, 6.261554119646462e-08, 0.0057148681953549385, 3.878555818664442e-15, 4.135955168749206e-05, 0.08881586790084839, 1.1112829169520558e-14, 0.10179802030324936, 4.583621385277712e-15, 0.22161994874477386, 8.940386171457041e-15, 1.3622869854206486e-14, 9.753131225006487e-15, 0.11474811285734177, 6.054923120372589e-15, 1.2532925645371545e-14, 1.0692334062416264e-14, 9.261815693182261e-15, 0.07775698602199554, 4.189427921735085e-15, 0.11154802143573761, 9.552231950576712e-15, 0.09227565675973892, 1.3862756361132482e-14, 7.464435496031159e-15, 0.10567525774240494, 8.156906106235231e-15, 0.1082899421453476, 0.09468618780374527, 0.09741327911615372, 0.006691036280244589, 0.080136239528656, 7.744179138290206e-15, 1.432254278556106e-14, 1.2255539295804706e-14, 0.16778193414211273, 1.15395719916438e-14, 0.23115557432174683, 0.22741453349590302, 0.22306445240974426, 0.020701326429843903, 0.06767397373914719, 0.21126964688301086, 8.98001884305907e-15, 6.511625921356689e-15, 0.10464271157979965, 0.0002463307464495301, 0.16718177497386932, 0.11474102735519409, 1.2057997659977848e-14, 0.09213186800479889, 0.10246744006872177, 0.015796341001987457, 0.1037309542298317, 0.0014164267340674996, 0.09771238267421722, 9.639334889641714e-15, 6.546211547142503e-15, 0.12635596096515656, 0.18353919684886932, 0.225483238697052, 0.10910467058420181, 0.08290110528469086, 0.09789011627435684, 1.1417722067016533e-14, 0.11245454847812653, 0.19034545123577118, 0.08208708465099335, 0.11215057224035263, 8.81765533256463e-15, 0.07349247485399246, 0.227248877286911, 0.10273955017328262, 1.3237362290021478e-14, 0.09614118188619614, 5.733362732057018e-15, 9.222705640908688e-15, 6.673515940433614e-15, 0.09930025041103363, 0.11285097897052765, 0.32163190841674805, 0.10284247994422913, 0.0005795400938950479, 0.11982789635658264, 0.11371953785419464, 0.1989048272371292, 0.21458366513252258, 0.08990844339132309, 0.0095727713778615, 0.09345372021198273, 7.338910295445755e-15, 4.1077078770498845e-15, 0.0963912159204483, 1.3221150926443978e-14, 0.10929552465677261, 1.506534832865572e-14, 1.2383875798742047e-14, 8.364435954576113e-15, 0.10650714486837387, 0.12681390345096588, 0.13760554790496826, 0.1180962547659874, 0.22121766209602356, 6.7700347900390625, 18.811405181884766, 5.13037109375, 12.818793296813965, 0.0, 6.345821857452393, 15.445140838623047, 3.860874652862549, 11.539764404296875, 4.185412883758545, 18.92877197265625, 2.3539106845855713, 6.620841979980469, 8.305313110351562, 7.648002624511719, 10.388503074645996, 10.960397720336914, 9.414740562438965, 6.158530235290527, 4.901975154876709, 4.2975921630859375, 3.6829349994659424, 5.01263427734375, 4.2301483154296875, 6.369147777557373, 5.800262451171875, 3.1889586448669434, 20.979961395263672, 5.308746337890625, 2.6100523471832275, 11.666400909423828, 4.8632659912109375, 3.3764877319335938, 3.3382420539855957, 0.8237457275390625, 6.318946361541748, 1.691847801208496, 4.307314872741699, 27.230985641479492, 7.340389251708984, 5.23046875, 6.122100830078125, 6.585409164428711, 7.833498477935791, 3.6520767211914062, 2.834853172302246, 16.756690979003906, 9.4462890625, 26.16212272644043, 12.413352966308594, 2.973384380340576, 3.147674560546875, 0.0, 3.515754222869873, 9.723997116088867, 0.0, 6.3081512451171875, 5.4650115966796875, 11.20377254486084, 8.663400650024414, 4.038848876953125, 1.5500411987304688, 3.718386650085449, 5.844474792480469, 4.601930618286133, 7.3356242179870605, 5.765666961669922, 6.285407543182373, 3.5212478637695312, 29.272817611694336, 1.826812744140625, 3.41259765625, 3.934009313583374, 8.178878784179688, 0.0, 7.030472278594971, 10.07769775390625, 5.586055755615234, 2.7281572818756104, 14.140098571777344, 4.4985809326171875, 10.965163230895996, 4.700813293457031, 3.973968744277954, 16.27033233642578, 2.6648266315460205, 6.014470100402832, 20.319631576538086, 4.824363708496094, 20.14966583251953, 7.9622955322265625, 7.908514022827148, 0.0, 18.498321533203125, 2.0927772521972656, 11.900221824645996, 8.013745307922363, 7.1669464111328125, 8.45965576171875, 0.0, 12.43613338470459, 6.580574989318848, 3.4387359619140625, 7.06721830368042, 4.3347320556640625, 9.961054801940918, 10.791831970214844, 1.9856518507003784, 3.7259674072265625, 10.987655639648438, 4.80645751953125, 3.0228588581085205, 3.211843490600586, 5.960319519042969, 4.3426971435546875, 14.998870849609375, 15.95316219329834, 5.521221160888672, 4.976585388183594, 21.30499267578125, 11.688761711120605, 3.020618200302124, 9.447654724121094, 5.852775573730469, 2.959458827972412, 5.0157084465026855, 2.920668840408325, 22.749069213867188, 4.021769046783447, 2.9794087409973145, 6.1438446044921875, 5.451211929321289, 5.835349082946777, 11.2435302734375, 6.180088996887207, 19.01692008972168, 0.0, 13.00559139251709, 4.5830230712890625, 6.76702880859375, 10.533525466918945, 8.829826354980469, 3.9287023544311523, 12.296844482421875, 8.050537109375, 17.92353630065918, 3.8794174194335938, 3.1882262229919434, 4.2495880126953125, 6.7356109619140625, 7.971336364746094, 7.79035758972168, 16.95759391784668, 1.7102851867675781, 0.0, 6.118947505950928, 6.714031219482422, 4.0225372314453125, 4.010307312011719, 7.022986888885498, 8.293136596679688, 9.980133056640625, 8.286949157714844, 4.88043212890625, 3.9000494480133057, 10.551971435546875, 8.72149658203125, 6.634083271026611, 12.582460403442383, 14.580986022949219, 8.087259292602539, 2.7532196044921875, 4.255332946777344, 6.487477779388428, 4.98652982711792, 6.392284393310547, 3.05426025390625, 5.184417724609375, 17.695941925048828, 11.721908569335938, 11.153661727905273, 8.421829223632812, 3.962616443634033, 20.79534912109375, 5.390274524688721, 20.106491088867188, 4.515899181365967, 35.75600814819336, 13.97519588470459, 31.31062889099121, 8.145008087158203, 4.4454803466796875, 2.6359846591949463, 3.86216402053833, 3.5293960571289062, 1.7358322143554688, 11.720770835876465, 24.85053825378418, 2.5942928791046143, 6.985955715179443, 1.2641525268554688, 5.634437084197998, 21.85464859008789, 12.591938018798828, 32.9481086730957, 8.989027976989746, 10.644035339355469, 3.6047990322113037, 6.8805389404296875, 10.149005889892578, 12.15506649017334, 5.766532897949219, 3.5746312141418457, 7.289573669433594, 22.247533798217773, 5.882309913635254, 6.270234107971191, 5.229580402374268, 10.14422607421875, 6.33476448059082, 7.62939453125e-06, 2.775266647338867, 4.803707122802734, 6.365641117095947, 2.0699615478515625, 25.93657684326172, 3.683351755142212, 3.8543474674224854, 9.349550247192383, 6.35160493850708, 3.448184013366699, 9.667916297912598, 0.0, 4.763343811035156, 2.7755608558654785, 10.02103328704834, 1.551920771598816, 1.913859486579895, 7.686614990234375, 6.846645355224609, 21.975067138671875, 18.24698257446289, 4.225974082946777, 4.3124542236328125, 8.101310729980469, 6.179553508758545, 8.071784019470215, 4.223733901977539, 22.233802795410156, 3.8832778930664062, 9.028021812438965, 9.925286293029785, 4.641322135925293, 8.431808471679688, 8.23282527923584, 3.1045074462890625, 12.619171142578125, 7.975199222564697, 10.92270565032959, 6.610546112060547, 4.295648574829102, 4.022171974182129, 5.760364055633545, 4.304779529571533, 12.288414001464844, 13.956260681152344, 4.300228118896484, 4.98748779296875, 9.079155921936035, 6.137580394744873, 12.027519226074219, 8.274864196777344, 4.863802909851074, 3.4129369258880615, 3.6919784545898438, 15.523948669433594, 19.191688537597656, 23.51161003112793, 7.3560791015625, 13.913593292236328, 7.491093158721924, 4.567694187164307, 7.610315799713135, 8.321541786193848, 2.805345058441162, 11.40280818939209, 10.286874771118164, 4.030094623565674, 0.0, 7.426719665527344, 22.421844482421875, 4.443359375, 14.765792846679688, 8.413186073303223, 13.902267456054688, 4.55661153793335, 2.618469476699829, 3.751270055770874, 3.5299551486968994, 0.0, 1.06279456615448, 1.4564608335494995, 0.8496418595314026, 1.3357343673706055, 0.0, 1.0423730611801147, 2.266160011291504, 1.4778753519058228, 0.892359733581543, 1.1659988164901733, 1.4203826189041138, 1.508414626121521, 1.3482465744018555, 1.2820183038711548, 2.4909753799438477, 1.384968638420105, 1.367181420326233, 9.5367431640625e-07, 1.7012128829956055, 9.5367431640625e-07, 2.064551591873169, 1.6769905090332031, 0.8122627139091492, 2.042527198791504, 9.5367431640625e-07, 1.5125455856323242, 2.7018041610717773, 2.0529491901397705, 2.7808566093444824, 0.4886627793312073, 0.0, 0.12708066403865814, 1.5065468549728394, 1.1864596605300903, 2.0172739028930664, 1.3560036420822144, 1.38521146774292, 2.042130708694458, 1.8976507186889648, 2.3792381286621094, 1.4250191450119019, 2.0814828872680664, 0.41714000701904297, 2.576892137527466, 1.436212182044983, 1.7900447845458984, 9.5367431640625e-07, 1.0934289693832397, 0.7715922594070435, 1.1386806964874268, 0.7018221616744995, 2.3609609603881836, 1.0320730209350586, 9.5367431640625e-07, 1.5016546249389648, 9.5367431640625e-07, 1.346030831336975, 1.7572507858276367, 1.51217520236969, 2.214616060256958, 1.2676420211791992, 1.2994095087051392, 0.7576932907104492, 9.5367431640625e-07, 1.3183106184005737, 0.7823813557624817, 0.8235329985618591, 2.876457452774048, 1.1263151168823242, 9.5367431640625e-07, 9.5367431640625e-07, 1.2652941942214966, 9.5367431640625e-07, 9.5367431640625e-07, 1.6356076002120972, 1.746821403503418, 1.455611228942871, 2.3289079666137695, 1.6954500675201416, 2.370906114578247, 3.4199588298797607, 1.8763914108276367, 1.3457021713256836, 9.5367431640625e-07, 1.555708885192871, 1.860370397567749, 9.5367431640625e-07, 1.8972941637039185, 2.3140947818756104, 1.7611075639724731, 1.3838582038879395, 1.6775158643722534, 9.5367431640625e-07, 1.3185166120529175, 0.0, 9.5367431640625e-07, 9.5367431640625e-07, 1.1975775957107544, 1.3944823741912842, 2.0621559619903564, 1.2043968439102173, 1.6576851606369019, 1.695109248161316, 0.880213737487793, 1.534196138381958, 2.4418368339538574, 1.3207656145095825, 9.5367431640625e-07, 1.0214539766311646, 1.2240084409713745, 1.3831437826156616, 0.975428581237793, 2.6153383255004883, 0.934018075466156, 2.0668530464172363, 1.1276044845581055, 1.6348509788513184, 9.5367431640625e-07, 1.497328758239746, 0.6414231061935425, 1.0688515901565552, 2.186918020248413, 1.877408742904663, 2.01560115814209, 1.5559319257736206, 1.6129205226898193, 1.6015726327896118, 1.8040783405303955, 9.5367431640625e-07, 9.5367431640625e-07, 1.2833703756332397, 2.0997421741485596, 0.5111856460571289, 2.0587880611419678, 1.158018708229065, 9.5367431640625e-07, 1.7773007154464722, 1.2077703475952148, 1.469799280166626, 1.1254013776779175, 9.5367431640625e-07, 1.8878637552261353, 1.3902863264083862, 1.2168529033660889, 0.0035893248859792948, 2.352604627609253, 1.5238981246948242, 1.3541653156280518, 9.5367431640625e-07, 1.8272945880889893, 1.7632821798324585, 1.6403913497924805, 1.8953884840011597, 1.0385535955429077, 2.0570099353790283, 9.5367431640625e-07, 1.5100265741348267, 1.6379873752593994, 1.6837763786315918, 0.0, 9.5367431640625e-07, 1.6850517988204956, 1.628277063369751, 0.8316909670829773, 1.0117254257202148, 1.2973828315734863, 1.0445876121520996, 1.0935561656951904, 9.5367431640625e-07, 1.6165881156921387, 1.288283348083496, 1.4786558151245117, 2.588932991027832, 9.5367431640625e-07, 0.8861804008483887, 2.0514163970947266, 2.045191764831543, 9.5367431640625e-07, 1.985481858253479, 0.9707596898078918, 1.4570493698120117, 9.5367431640625e-07, 1.4877938032150269, 2.0354979038238525, 1.5808809995651245, 1.6555309295654297, 1.3967429399490356, 1.2141706943511963, 0.6437501311302185, 1.8961248397827148, 1.0641289949417114, 1.1063851118087769, 9.5367431640625e-07, 1.9575508832931519, 1.7883620262145996, 9.5367431640625e-07, 1.54243004322052, 1.0813263654708862, 1.2615631818771362, 9.5367431640625e-07, 0.9049791693687439, 1.6972646713256836, 2.2973670959472656, 1.263338565826416, 1.318125605583191, 1.4263830184936523, 1.7655487060546875, 1.2606160640716553, 1.8745718002319336, 0.6887571811676025, 1.6039036512374878, 2.488004446029663, 0.007422866765409708, 0.7843777537345886, 1.1186819076538086, 1.8511959314346313, 0.820266842842102, 9.5367431640625e-07, 1.811232089996338, 9.5367431640625e-07, 0.8956547975540161, 1.512292504310608, 2.1119847297668457, 1.8412749767303467, 1.1391842365264893, 1.0962631702423096, 2.899805784225464, 0.9165620803833008, 9.5367431640625e-07, 1.900156855583191, 1.23192298412323, 1.9305777549743652, 9.5367431640625e-07, 9.5367431640625e-07, 9.5367431640625e-07, 2.1366493701934814, 0.19414298236370087, 1.044442057609558, 1.2934311628341675, 0.4766817092895508, 0.9672274589538574, 1.3908724784851074, 0.9368417263031006, 1.8001585006713867, 1.4736393690109253, 9.5367431640625e-07, 0.6709699630737305, 9.5367431640625e-07, 1.295093059539795, 9.5367431640625e-07, 9.5367431640625e-07, 1.2384594678878784, 1.45862877368927, 1.8404358625411987, 1.223655343055725, 9.5367431640625e-07, 2.173462390899658, 0.36990073323249817, 1.8219841718673706, 2.0970354080200195, 1.6169060468673706, 1.2718688249588013, 1.6661367416381836, 1.8196206092834473, 1.9346102476119995, 9.5367431640625e-07, 1.613814353942871, 0.9946946501731873, 1.365889549255371, 1.4009885787963867, 1.8779217004776, 2.528838634490967, 0.7115378379821777, 1.6814624071121216, 9.5367431640625e-07, 2.591306686401367, 0.18156909942626953, 1.850172996520996, 9.5367431640625e-07, 0.12883301079273224, 1.6976526975631714, 1.4424892663955688, 1.4330642223358154, 2.0016164779663086, 1.3831356763839722, 0.7524880766868591, 1.4705686569213867, 9.5367431640625e-07, 1.4539945125579834, 0.06550312042236328, 9.5367431640625e-07, 2.3543291091918945, 1.8983124494552612, 1.160231590270996, 1.1911782026290894, 0.743464469909668, 1.3548134565353394, 1.7744768857955933, 9.5367431640625e-07, 9.5367431640625e-07, 0.0, 0.0, 0.0, 0.0, 0.019904255867004395, 0.008856773376464844, 0.0, 0.023173987865447998, 0.0004634368233382702, 0.01315505150705576, 0.0, 0.0016925281379371881, 0.0, 0.0, 0.02227938175201416, 0.0003876936389133334, 0.00030793010955676436, 0.0, 0.0, 0.0, 0.022211356088519096, 7.1525572131747595e-09, 0.0, 0.0, 0.0, 5.9604643443123e-10, 0.008957336656749249, 0.022524535655975342, 0.017845964059233665, 0.003463927423581481, 0.0, 0.06847739219665527, 7.152557373046875e-07, 0.00034791050711646676, 0.0, 0.004724760074168444, 0.006603802088648081, 0.0, 0.0, 0.05185878649353981, 0.016659319400787354, 0.0, 0.005939444061368704, 0.0, 0.0, 2.64775753748836e-05, 0.016607582569122314, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0025815963745117188, 0.062101658433675766, 5.9604643443123e-10, 0.009677254594862461, 0.0, 0.0, 0.0, 0.062101658433675766, 0.00033162414911203086, 0.0, 1.19209286886246e-09, 0.0, 0.0, 0.0, 0.0, 0.0, 0.001542508602142334, 0.0, 0.023048045113682747, 0.0033818762749433517, 0.006251882296055555, 0.02355213277041912, 0.003010571002960205, 0.0, 0.0, 0.0, 0.0, 0.0007265311433002353, 0.0, 0.0, 0.005535993259400129, 0.0, 0.0, 0.0, 0.0, 0.006403748877346516, 0.0020043777767568827, 0.0, 0.0, 0.0, 0.03343290090560913, 0.06747207045555115, 2.3782253322224278e-07, 0.007850885391235352, 0.05693064630031586, 5.9604643443123e-10, 0.0, 0.0, 5.0786733481800184e-05, 0.0, 0.0, 0.000779271125793457, 0.003097184933722019, 0.036181703209877014, 0.0026907920837402344, 0.017846407368779182, 0.0, 0.0018987166695296764, 0.0, 0.003650564467534423, 0.0010535860201343894, 0.0, 0.0, 0.009135699830949306, 0.0, 0.0, 0.0, 0.018839308992028236, 0.003736262209713459, 0.0, 0.0498347282409668, 0.0, 0.0, 0.00016107498959172517, 0.002098679542541504, 0.03141472861170769, 0.001129217678681016, 0.0, 0.0073575121350586414, 0.00012351035547908396, 0.0, 0.0, 7.411300612147897e-05, 0.0, 0.001148234587162733, 0.03814932703971863, 9.969413076760247e-05, 4.404068022267893e-05, 0.0, 0.0, 0.024880370125174522, 0.02350795455276966, 0.0, 0.003086273092776537, 2.7592181140789762e-05, 0.0, 0.0, 0.0, 0.0, 0.003589017316699028, 4.607439052506379e-07, 0.0, 0.02073890157043934, 0.012666341848671436, 0.0, 0.0, 0.0014370703138411045, 0.0, 0.00406554015353322, 0.0020349090918898582, 0.011127416975796223, 0.0, 0.0, 0.0, 0.0012286901473999023, 0.008483641780912876, 0.0, 0.0, 0.0, 0.0011074661742895842, 0.0, 0.0, 0.0, 0.001068706507794559, 0.0, 0.026143187656998634, 0.0014889108715578914, 0.0006179213523864746, 0.0017067223088815808, 0.0005241656326688826, 0.0, 0.0, 0.0, 0.004305856768041849, 5.364418029785156e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0001537662756163627, 0.0051540806889534, 0.0, 0.0, 0.0, 0.0, 0.00733855040743947, 0.057356927543878555, 0.000837579951621592, 0.0, 0.0035933065228164196, 0.0, 0.05529302358627319, 0.03917296603322029, 0.03262120485305786, 0.0037719623651355505, 0.000369630433851853, 0.04497357830405235, 2.944469486010348e-07, 0.0, 0.0018636333988979459, 0.0, 0.0, 0.029664112254977226, 0.02133828029036522, 0.0, 0.0, 0.0, 0.0, 0.000979006290435791, 4.467367944016587e-06, 0.0, 0.0, 0.0018332707695662975, 2.4622677301522344e-05, 0.0008776164031587541, 0.00785194244235754, 0.007636010646820068, 0.0, 0.014260243624448776, 0.0, 0.0, 0.05599820986390114, 0.0, 0.002964165061712265, 0.0, 0.006823718547821045, 0.010037330910563469, 0.0, 0.0, 0.01625230349600315, 0.0, 0.0, 0.00650055892765522, 0.0, 0.008653929457068443, 0.0, 1.1920928955078125e-07, 0.015972409397363663, 0.0386805534362793, 0.0034069488756358624, 0.0, 0.0, 0.0, 0.01126356702297926, 0.0, 0.0, 0.005292326211929321, 0.02913755737245083, 0.01028353814035654, 0.00011658668518066406, 0.0, 5.1150320359738544e-05, 0.0706067904829979, 9.208917617797852e-05, 0.0, 0.0019658803939819336, 0.0032878518104553223, 0.0005156183033250272, 0.005674958229064941, 0.0, 0.005226921755820513, 4.1734576370799914e-05, 8.970975613920018e-05, 8.947848982643336e-06, 0.0, 4.0588973206467927e-05, 0.0, 0.0, 0.0035200731363147497, 0.0, 0.0, 0.0, 0.0, 0.00029861927032470703, 0.0, 0.0, 0.03371217101812363, 0.07075915485620499, 0.02664083242416382, 5.603015233646147e-05, 0.0, 0.011326787061989307, 0.0, 0.10118669271469116, 0.00010036263120127842, 0.11729881167411804, 0.08746673166751862, 0.339913934469223, 0.013622195459902287, 0.0927228108048439, 9.467301651021418e-15, 4.617692862064543e-15, 0.2182842195034027, 0.12120529264211655, 0.08410684764385223, 0.09335637092590332, 0.08089309185743332, 0.22215911746025085, 0.11172187328338623, 0.22822928428649902, 0.23288924992084503, 0.12333574146032333, 0.021140122786164284, 1.5037709643586812e-14, 8.853411134367075e-15, 0.1008392721414566, 0.1128634437918663, 0.16605179011821747, 0.0909351110458374, 0.0833275318145752, 0.09605865925550461, 0.11831563711166382, 5.0475468362030495e-15, 0.04894319921731949, 0.1086898222565651, 0.23690055310726166, 0.13796454668045044, 0.17499931156635284, 8.52968784742069e-15, 1.1002311698694606e-14, 1.4541160295181502e-14, 0.08985643833875656, 0.1173662543296814, 3.881683064305705e-15, 0.00943954661488533, 0.10240743309259415, 0.09351086616516113, 0.1106356754899025, 0.10886648297309875, 0.10427087545394897, 0.0009027157793752849, 0.005816766992211342, 0.1842583864927292, 0.12988528609275818, 0.11663051694631577, 0.09089341759681702, 0.1159849539399147, 0.19954364001750946, 0.1051817461848259, 0.0015484431060031056, 0.2579179108142853, 0.21991747617721558, 0.08438585698604584, 0.0006753302877768874, 5.197332330947237e-15, 0.005175018683075905, 0.21989107131958008, 0.11515222489833832, 0.23676283657550812, 0.005341889802366495, 0.07744057476520538, 0.0980263277888298, 0.024309782311320305, 1.0948664019947308e-14, 7.506957397016272e-15, 6.3273339984072554e-15, 0.08964775502681732, 0.1435193419456482, 0.09395661950111389, 0.09828940778970718, 0.059320367872714996, 0.1089460477232933, 0.10220333188772202, 1.1268883131590902e-14, 0.13512012362480164, 6.107569182659759e-15, 0.11544974893331528, 1.193137216359396e-14, 1.2516544875204594e-14, 0.16736163198947906, 6.41597853743626e-15, 0.11091651767492294, 4.338786088357383e-15, 5.3895156363497655e-15, 1.3754154031800272e-14, 1.266783766507842e-14, 0.048106539994478226, 0.1578199714422226, 1.4820881067550973e-14, 7.229616787228586e-15, 9.517236784360901e-15, 0.10202990472316742, 0.09809621423482895, 0.09696338325738907, 0.09167245775461197, 0.04603970795869827, 0.1062091812491417, 0.0028004618361592293, 0.13979125022888184, 0.07280593365430832, 0.11282340437173843, 0.23371516168117523, 0.0799725204706192, 0.09611283987760544, 0.09290457516908646, 9.172708674164056e-15, 0.24476107954978943, 6.636224044381323e-15, 0.10404843837022781, 0.10963144153356552, 0.003611424472182989, 0.08514977991580963, 0.08774236589670181, 6.577809264206877e-15, 1.0865310895739801e-14, 0.22390678524971008, 9.060857973479126e-15, 4.514345525137098e-15, 0.12499262392520905, 0.09949040412902832, 1.1650507049712749e-14, 0.08181123435497284, 0.11535743623971939, 0.09610500186681747, 0.08823633193969727, 0.019537746906280518, 1.2766803300569719e-14, 1.5063013905853087e-14, 0.111307293176651, 0.08246159553527832, 0.08258526027202606, 0.12116070836782455, 5.2997894362471175e-15, 0.13558512926101685, 4.809669067911467e-15, 0.10491378605365753, 0.32941606640815735, 0.17906545102596283, 0.11439593881368637, 0.0979427918791771, 0.21916620433330536, 0.185287743806839, 0.10254377126693726, 0.001374275190755725, 0.08633124828338623, 1.439758482249011e-14, 0.13484390079975128, 0.12050250917673111, 1.054127505363588e-14, 0.09121385216712952, 0.09943795204162598, 0.11359675973653793, 0.2238500863313675, 1.189059853861198e-14, 0.09507220983505249, 0.13034074008464813, 0.23451346158981323, 7.969592393246468e-15, 0.10893648862838745, 7.837798301818435e-15, 0.15212661027908325, 1.4994477081958953e-14, 0.05920260399580002, 6.47489476111548e-15, 6.478472204768208e-15, 0.10830499231815338, 1.5163588903944168e-14, 0.0027240763884037733, 0.20548221468925476, 0.11293672025203705, 0.0949452668428421, 0.174135223031044, 0.09151197969913483, 9.93044994921765e-15, 0.10616520792245865, 0.11723943799734116, 0.013135263696312904, 0.10344184935092926, 0.09623507410287857, 0.10446342080831528, 0.10799607634544373, 1.1483574643500818e-14, 0.09258762001991272, 0.10677001625299454, 1.1503491776222556e-14, 0.009610099717974663, 0.20049598813056946, 0.35543784499168396, 0.09289482980966568, 1.3607649519177274e-14, 0.0003105423238594085, 4.9983638681207285e-15, 5.0805421576303935e-15, 4.796047507570197e-15, 0.2280968427658081, 0.19166997075080872, 0.11697456240653992, 4.0758721437273316e-15, 0.06832410395145416, 0.040135450661182404, 6.3271442630270704e-15, 0.09489652514457703, 0.08905744552612305, 7.983811535332026e-15, 0.15126407146453857, 5.652011570220347e-15, 8.198311617795863e-15, 5.722695199119297e-15, 0.08997222036123276, 4.507246118489686e-15, 0.09847637265920639, 0.23112042248249054, 0.11252138018608093, 0.021216213703155518, 0.0017432678723707795, 0.09605642408132553, 0.27099597454071045, 0.21902421116828918, 0.012117988429963589, 0.21551649272441864, 0.068178191781044, 0.13744324445724487, 1.0650793872617019e-14, 6.4856973958082875e-15, 0.09063860028982162, 0.0011902828700840473, 7.820742446392522e-15, 1.0922525430227988e-14, 3.8371638596309664e-15, 0.0841093584895134, 0.19762618839740753, 0.0895681381225586, 0.16926291584968567, 0.09867080301046371, 0.005946481134742498, 0.09207215905189514, 0.09017784148454666, 4.493460233756649e-15, 0.09151879698038101, 0.03451165556907654, 0.08286452293395996, 0.09928485006093979, 0.08243589103221893, 0.0793670266866684, 0.11121711134910583, 0.09267593175172806, 0.09361013025045395, 0.1469648778438568, 0.006776028778403997, 0.04620019346475601, 0.007447360549122095, 0.09056423604488373, 0.219626784324646, 0.30228307843208313, 8.96983242483539e-15, 1.0085949104707542e-14, 6.391709772948003e-15, 0.1116543710231781, 0.23419544100761414, 1.0417794590585148e-14, 0.10345277190208435, 0.23755884170532227, 1.1901785302746368e-14, 0.015863094478845596, 5.767337223571388e-15, 6.2784906905367834e-15, 0.19646628201007843, 1.3048175787186336e-14, 0.11322444677352905, 0.09629140794277191, 0.04228050634264946, 0.05765661597251892, 0.09895286709070206, 0.09537569433450699, 0.08054046332836151, 0.10459250211715698, 1.5114945495849248e-14, 0.1086665689945221, 0.0945296436548233, 6.5494243431114384e-15, 0.1170695573091507, 0.002509084530174732, 0.31034255027770996, 0.19188539683818817, 0.11399906873703003, 0.09613174200057983, 1.1765477372742417e-14, 1.3333918116777838e-14, 0.09476976096630096, 0.21804176270961761, 1.0697161303182667e-14, 7.767893519714485e-15, 0.007538068573921919, 5.006869792938232, 5.8394317626953125, 5.8797607421875, 5.604081153869629, 7.2143402099609375, 13.292572021484375, 15.296095848083496, 3.6167900562286377, 2.6459152698516846, 10.193163871765137, 9.764972686767578, 2.9912033081054688, 16.33887481689453, 6.83319091796875, 23.312124252319336, 6.04736328125, 11.717880249023438, 6.310524940490723, 16.49623680114746, 13.477670669555664, 6.974208831787109, 2.8083724975585938, 5.011207580566406, 14.976133346557617, 13.432787895202637, 6.223580360412598, 8.637222290039062, 6.151843547821045, 8.423282623291016, 7.038604736328125, 18.011476516723633, 6.548057556152344, 5.588852405548096, 3.8805015087127686, 7.517197132110596, 12.5010986328125, 4.2820353507995605, 1.9283736944198608, 19.804351806640625, 15.659149169921875, 10.236628532409668, 11.409804344177246, 16.161300659179688, 13.233034133911133, 36.88015365600586, 5.0446319580078125, 1.5115150213241577, 2.5911645889282227, 8.156753540039062, 13.16461181640625, 1.360954999923706, 6.6149444580078125, 9.175811767578125, 16.19414520263672, 11.874282836914062, 4.028676509857178, 12.199447631835938, 4.035736083984375, 10.850143432617188, 27.122726440429688, 17.24897003173828, 7.831287860870361, 17.02819061279297, 2.4991989135742188, 5.148571491241455, 3.05352783203125, 3.6771907806396484, 3.973297119140625, 2.1627211570739746, 10.99361801147461, 16.844772338867188, 5.914726257324219, 10.77105712890625, 8.329952239990234, 4.177040100097656, 6.015525817871094, 7.409877777099609, 7.447344779968262, 4.5066914558410645, 3.612689733505249, 3.17508602142334, 6.036940574645996, 10.318346977233887, 5.10992431640625, 21.512601852416992, 10.529541015625, 5.034980297088623, 3.2113037109375, 6.892265319824219, 5.195563793182373, 8.0157470703125, 5.410394191741943, 2.6409802436828613, 8.9390869140625, 6.019744873046875, 5.673560619354248, 6.811027526855469, 4.005279541015625, 5.000558853149414, 5.261231422424316, 7.493261337280273, 4.201820373535156, 5.383022308349609, 13.022172927856445, 5.449642181396484, 2.359800100326538, 15.459701538085938, 7.139035701751709, 29.022132873535156, 8.853949546813965, 8.663078308105469, 8.517324447631836, 10.488273620605469, 6.940375804901123, 6.324737548828125, 6.342696189880371, 8.950678825378418, 6.713343143463135, 5.353248119354248, 42.1443977355957, 3.300781488418579, 2.9776670932769775, 7.8215179443359375, 3.981548309326172, 16.99286651611328, 4.515085220336914, 5.4706268310546875, 3.329745292663574, 8.200029373168945, 0.752876341342926, 6.079958438873291, 9.432662963867188, 8.679022789001465, 6.381542205810547, 11.476066589355469, 20.36219596862793, 3.1985435485839844, 11.158935546875, 25.17976951599121, 5.4177117347717285, 4.960419654846191, 2.0749573707580566, 5.477485179901123, 6.388710975646973, 8.841768264770508, 5.387187957763672, 10.424272537231445, 6.5442352294921875, 5.041879177093506, 8.90411376953125, 6.1005706787109375, 14.257084846496582, 4.752108573913574, 4.3458251953125, 15.3687744140625, 22.69227409362793, 7.943321228027344, 15.313949584960938, 3.0517577442878974e-07, 5.242194652557373, 12.5106201171875, 17.234514236450195, 3.9888482093811035, 6.524081707000732, 3.0914764404296875, 27.881263732910156, 8.086787223815918, 2.3439459800720215, 12.375432014465332, 6.975494384765625, 6.1435089111328125, 8.542434692382812, 9.725099563598633, 15.78510856628418, 4.035301208496094, 8.662765502929688, 4.06256103515625, 5.65472412109375, 10.393051147460938, 6.030754089355469, 16.78216552734375, 4.334200382232666, 6.248579025268555, 5.9294352531433105, 8.080429077148438, 1.9280489683151245, 3.6834640502929688, 17.434539794921875, 15.05213451385498, 6.181475639343262, 8.491889953613281, 4.182746887207031, 10.230827331542969, 5.76068115234375, 21.00604248046875, 6.916572093963623, 5.121131420135498, 5.8331146240234375, 2.15997314453125, 3.50457763671875, 4.834159851074219, 6.396691799163818, 3.0648930072784424, 5.118316650390625, 7.92596435546875, 9.055754661560059, 3.0713272094726562, 4.129890441894531, 32.17134094238281, 5.100915908813477, 7.191619873046875, 4.43663215637207, 5.218024730682373, 9.645044326782227, 2.8481216430664062, 31.463205337524414, 9.428351402282715, 4.963540554046631, 6.710840702056885, 6.552891254425049, 8.001761436462402, 11.345778465270996, 8.485370635986328, 23.148555755615234, 11.027289390563965, 7.786990165710449, 6.9952545166015625, 6.255363464355469, 19.86853790283203, 5.737891674041748, 8.272979736328125, 12.870895385742188, 6.662432670593262, 8.820209503173828, 10.171112060546875, 10.071600914001465, 18.24040985107422, 12.06400203704834, 20.08106231689453, 3.4795873165130615, 3.4682769775390625, 8.087114334106445, 9.940605163574219, 15.30356502532959, 4.611838340759277, 11.677934646606445, 10.030685424804688, 9.470001220703125, 9.659305572509766, 7.005115985870361, 6.6946258544921875, 6.882469177246094, 8.383079528808594, 16.4677734375, 12.258563995361328, 25.875761032104492, 16.60992431640625, 6.032747268676758, 4.252891540527344, 5.66550874710083, 4.028176784515381, 15.104262351989746, 4.5750885009765625, 5.493869304656982, 3.22973370552063, 6.56292724609375, 5.975471019744873, 8.092086791992188, 17.678993225097656, 4.648735046386719, 8.079246520996094, 5.036659240722656, 13.72580623626709, 7.887012958526611, 5.361663818359375, 15.616302490234375, 4.405601501464844, 12.259490966796875, 10.52640438079834, 6.614555358886719, 8.185431480407715, 9.014114379882812, 2.6741857528686523, 6.349128246307373, 4.35968017578125, 14.19459056854248, 7.62939453125e-06, 12.19818115234375, 39.98972702026367, 14.582106590270996, 8.148269653320312, 2.003143310546875, 10.78501033782959, 9.055290222167969, 6.956787109375, 19.590301513671875, 11.409820556640625, 10.229975700378418, 7.442430019378662, 4.985395908355713, 1.443617820739746, 1.4376314878463745, 1.6562633514404297, 1.3581360578536987, 9.5367431640625e-07, 1.3621021509170532, 1.0546064376831055, 1.145211100578308, 1.0299813747406006, 0.7202978134155273, 9.5367431640625e-07, 2.1344003677368164, 0.3166170120239258, 2.04831600189209, 2.4474093914031982, 1.5488728284835815, 0.0, 1.5247775316238403, 1.2442655563354492, 1.259695053100586, 1.8133649826049805, 1.6835637092590332, 0.9058884978294373, 1.8119382858276367, 1.687050700187683, 0.0, 0.3234415054321289, 1.8598815202713013, 1.674015760421753, 1.2615302801132202, 1.5204592943191528, 1.5275391340255737, 2.2231557369232178, 1.1575191020965576, 1.36285400390625, 1.8191092014312744, 1.052547574043274, 2.1056833267211914, 1.2910528182983398, 1.7930117845535278, 1.4549683332443237, 1.6986876726150513, 2.17063307762146, 1.3167732954025269, 1.8298064470291138, 9.5367431640625e-07, 2.7583160400390625, 1.3207372426986694, 2.4313437938690186, 9.5367431640625e-07, 9.5367431640625e-07, 1.6183959245681763, 1.2908295392990112, 1.6437047719955444, 2.944669008255005, 1.2245512008666992, 0.0, 1.0987005233764648, 0.031010398641228676, 2.587115526199341, 1.6664055585861206, 9.5367431640625e-07, 1.8119667768478394, 1.6207243204116821, 1.5125417709350586, 1.168562889099121, 1.0586271286010742, 1.9872679710388184, 2.686312437057495, 1.66844642162323, 0.924229621887207, 1.2431498765945435, 9.5367431640625e-07, 9.5367431640625e-07, 1.6481658220291138, 0.17300131916999817, 1.8972680568695068, 1.905587077140808, 1.9323132038116455, 1.145186424255371, 9.5367431640625e-07, 2.6853740215301514, 9.5367431640625e-07, 1.4146515130996704, 1.9391487836837769, 1.0722417831420898, 1.6362122297286987, 9.5367431640625e-07, 2.2913527488708496, 2.5858054161071777, 1.478274941444397, 1.9335994720458984, 3.1861681938171387, 9.5367431640625e-07, 0.9078111052513123, 2.1503143310546875, 0.023796863853931427, 9.5367431640625e-07, 0.1919412612915039, 2.1368134021759033, 1.710139274597168, 1.4252374172210693, 1.0676345825195312, 1.4757190942764282, 1.5845414400100708, 2.8753387928009033, 0.7673177719116211, 2.225769281387329, 1.1826014518737793, 1.1143501996994019, 1.2829025983810425, 0.7374181747436523, 1.131949543952942, 1.9634157419204712, 0.851276695728302, 1.818203330039978, 1.6157959699630737, 1.4980477094650269, 1.0514745712280273, 1.32138192653656, 2.4877002239227295, 1.4670838117599487, 1.0554940700531006, 2.6720025539398193, 1.9911482334136963, 1.9432485103607178, 1.3361949920654297, 1.803597331047058, 1.2229670286178589, 2.11673641204834, 1.8921819925308228, 9.5367431640625e-07, 1.6341924667358398, 2.3382835388183594, 2.319160223007202, 1.5263668298721313, 2.134176254272461, 9.5367431640625e-07, 1.2173432111740112, 1.51884925365448, 1.2881008386611938, 1.9407051801681519, 1.131881594657898, 9.5367431640625e-07, 1.524347186088562, 1.235373616218567, 1.247683048248291, 1.6415575742721558, 0.41674327850341797, 1.2352590560913086, 1.3956729173660278, 1.452375054359436, 1.078225016593933, 1.262459635734558, 1.0186097621917725, 2.507596015930176, 1.1853970289230347, 1.6644010543823242, 0.4983349144458771, 1.4646309614181519, 0.02784442901611328, 1.6380600929260254, 1.2774258852005005, 0.3786727488040924, 2.178542137145996, 0.0, 1.9929113388061523, 1.5837807655334473, 1.4690366983413696, 1.3298821449279785, 1.5850412845611572, 9.5367431640625e-07, 9.5367431640625e-07, 2.120342254638672, 2.1052701473236084, 0.43615055084228516, 1.0489377975463867, 9.5367431640625e-07, 1.1220388412475586, 9.5367431640625e-07, 1.6395105123519897, 9.5367431640625e-07, 2.370633125305176, 1.544716715812683, 1.6322983503341675, 1.669537901878357, 1.6295839548110962, 1.7561979293823242, 2.2457878589630127, 9.5367431640625e-07, 1.604628562927246, 9.5367431640625e-07, 1.1239310503005981, 9.5367431640625e-07, 1.7322334051132202, 1.7614983320236206, 1.693109393119812, 0.8225564360618591, 1.214907169342041, 1.5878807306289673, 0.16623403131961823, 2.2741270065307617, 1.6352988481521606, 1.6814346313476562, 0.7766942977905273, 0.752314567565918, 2.1986498832702637, 1.706618309020996, 2.1115357875823975, 2.01052188873291, 1.6056394577026367, 0.9837369322776794, 1.8715893030166626, 1.177381992340088, 1.6526376008987427, 1.4363983869552612, 9.5367431640625e-07, 9.5367431640625e-07, 0.7497147917747498, 2.5747058391571045, 1.2356728315353394, 0.23390674591064453, 1.2341536283493042, 0.06820392608642578, 2.254607915878296, 2.3415918350219727, 1.4595837593078613, 2.0442087650299072, 1.668025016784668, 2.1858816146850586, 9.5367431640625e-07, 1.048485279083252, 2.4588418006896973, 1.5115063190460205, 0.7778303623199463, 0.8414273858070374, 0.7388848662376404, 1.7007027864456177, 1.3857444524765015, 1.7773854732513428, 0.548808217048645, 0.027411460876464844, 1.251007318496704, 0.020772438496351242, 1.0810898542404175, 1.0942754745483398, 9.5367431640625e-07, 1.795780897140503, 1.8202029466629028, 1.6956524848937988, 1.178297758102417, 2.3477373123168945, 1.8953956365585327, 1.9591702222824097, 1.7029855251312256, 0.5193471908569336, 1.853008508682251, 1.1887065172195435, 1.240792989730835, 0.9153773188591003, 1.1589363813400269, 1.05547034740448, 1.1582987308502197, 1.950863242149353, 1.9744387865066528, 1.4979676008224487, 2.082435369491577, 1.126773715019226, 1.112877607345581, 2.0772759914398193, 1.629958152770996, 2.270115613937378, 9.5367431640625e-07, 9.5367431640625e-07, 2.0653722286224365, 2.218440055847168, 1.3413909673690796, 1.4689054489135742, 1.0033354759216309, 1.1725307703018188, 1.0265963077545166, 1.762385368347168, 2.239509105682373, 0.8752727508544922, 1.393510103225708, 9.5367431640625e-07, 0.9942388534545898, 1.705979824066162, 1.335230827331543, 1.3277180194854736, 0.6739654541015625, 9.5367431640625e-07, 1.1286497116088867, 9.5367431640625e-07, 9.5367431640625e-07, 2.049118757247925, 9.5367431640625e-07, 1.5062932968139648, 9.5367431640625e-07, 2.455942153930664, 0.002564696129411459, 0.0, 0.0, 0.01056485716253519, 0.0, 0.0, 0.003779057879000902, 0.045361220836639404, 0.012199990451335907, 0.001669529010541737, 0.002652470488101244, 0.0, 0.0011983060976490378, 0.0004814684216398746, 0.0, 0.004532454535365105, 0.005584359169006348, 0.0, 0.00013020574988331646, 0.007161139510571957, 0.0, 0.00017834961181506515, 2.9087066195643274e-06, 0.0498347282409668, 0.002063630148768425, 0.0, 0.0, 0.0, 0.0, 0.00039310037391260266, 0.0, 2.093732291541528e-05, 0.006238043308258057, 0.007460960187017918, 0.0005893707275390625, 0.0015630722045898438, 0.0021274792961776257, 0.0, 0.011067092418670654, 0.04466173052787781, 0.0, 0.0, 0.0012508034706115723, 0.0, 0.0008309173281304538, 0.0, 0.0005863248952664435, 0.0643499419093132, 0.011785924434661865, 0.04886115342378616, 0.03322536498308182, 0.00031365870381705463, 0.02090895175933838, 0.01899881102144718, 0.00012100696039851755, 0.0, 0.0, 0.017301559448242188, 0.012250521220266819, 0.0, 0.05529302358627319, 0.0, 0.0, 0.0002804130199365318, 0.006701629143208265, 0.0022493600845336914, 0.0007842862396501005, 4.611611439031549e-05, 0.07083267718553543, 0.006031193770468235, 0.0, 5.364418029785156e-07, 0.0, 0.006903423462063074, 0.0, 0.045361220836639404, 0.029840420931577682, 0.015141620300710201, 0.024493541568517685, 0.0, 0.04159289225935936, 0.0, 1.6545056496397592e-05, 0.024392297491431236, 0.016278445720672607, 0.004505522549152374, 0.05862525478005409, 0.012448582798242569, 0.01424382533878088, 0.00034949122346006334, 0.0, 0.0, 0.0, 0.0, 4.188954699202441e-05, 0.0001694566017249599, 0.0, 0.004693210124969482, 0.008672809228301048, 0.004048477858304977, 0.0, 0.006629534997045994, 0.019747333601117134, 0.0002659821475390345, 0.00014770030975341797, 0.017559409141540527, 0.0, 0.0009260934311896563, 0.0, 0.00018638372421264648, 0.0, 0.0, 0.0, 0.008616604842245579, 0.03223177418112755, 0.0, 0.0, 0.001901095500215888, 0.0, 0.0032684551551938057, 0.0, 0.04536330699920654, 0.00975059624761343, 0.042724788188934326, 0.0003407764306757599, 4.850089317187667e-05, 0.012440265156328678, 0.0, 0.00834750384092331, 0.0, 0.002136051654815674, 0.010323762893676758, 0.0, 0.0, 0.01066617015749216, 0.0, 0.000503838062286377, 0.01590852253139019, 0.062101658433675766, 0.00023050665913615376, 0.0, 8.14950471976772e-05, 3.659725109628198e-07, 0.045361220836639404, 0.01087433286011219, 0.0, 0.0, 0.0, 0.002793624997138977, 0.0, 0.045361220836639404, 0.0, 0.00024688243865966797, 0.0, 0.05529302358627319, 0.04537397250533104, 0.007255492266267538, 7.800757884979248e-05, 2.8612612368306145e-05, 0.0, 0.0, 0.0, 0.003372500417754054, 5.9604643443123e-10, 0.0, 0.0010260611306875944, 0.0, 0.0056477258913218975, 0.0, 5.9604643443123e-10, 0.0, 0.006903409957885742, 0.013826324604451656, 0.007626226171851158, 0.0, 0.007525751832872629, 0.018909474834799767, 0.036406490951776505, 0.05010795593261719, 0.045361220836639404, 0.00012327313015703112, 0.01673770137131214, 0.0012481820303946733, 0.045361220836639404, 0.0, 0.0008957618265412748, 5.9604643443123e-10, 0.0, 0.0, 7.516145706176758e-05, 0.0019349455833435059, 0.0, 0.0, 0.00015419721603393555, 0.03579743206501007, 0.003567606210708618, 0.0018343335250392556, 0.0, 0.00038218675763346255, 0.04915153980255127, 0.00943101104348898, 0.0037332354113459587, 0.0, 2.324581060975106e-08, 2.6226043701171875e-06, 0.034142378717660904, 0.0, 0.0, 3.5762786065873797e-09, 0.057233113795518875, 0.0, 0.0, 0.019197583198547363, 0.0, 0.00526464032009244, 0.0, 0.0062360879965126514, 0.0, 0.0, 0.0, 0.0, 0.0028547989204525948, 0.0, 0.0014693158445879817, 0.0, 5.565166429732926e-05, 0.0028790836222469807, 0.006076214835047722, 0.004873125813901424, 0.0, 0.000979179167188704, 0.011657957918941975, 0.0, 0.0, 0.028974274173378944, 0.004158037714660168, 0.0, 0.02000165358185768, 0.006968971341848373, 0.0, 0.0002520477573852986, 0.0, 0.002807055599987507, 2.3000835426501e-05, 6.175458111101761e-05, 0.0, 0.0, 0.008471488952636719, 0.024571001529693604, 8.976459184850683e-07, 0.0, 0.052948374301195145, 8.77410129760392e-05, 0.006851364392787218, 0.023036250844597816, 0.06847889721393585, 0.005130123347043991, 0.0007107853889465332, 3.124952127109282e-05, 0.0, 1.5497207641601562e-06, 0.0091441310942173, 0.0, 0.00629514129832387, 0.0, 0.0, 0.0, 0.033775024116039276, 0.001057816669344902, 0.0, 0.0, 0.000935683841817081, 0.0, 0.0, 0.0038007544353604317, 0.0, 0.00028014183044433594, 0.00683516263961792, 0.0, 0.014079689979553223, 0.0, 3.045558878511656e-05, 0.0021474247332662344, 0.0, 0.0063147591426968575, 0.0, 0.011178834363818169, 0.013552248477935791, 0.0003177159815095365, 0.008371981792151928, 0.0, 0.001152520184405148, 0.0, 0.014737178571522236, 0.04831809550523758, 0.0028777122497558594, 0.018255535513162613, 0.0, 0.0, 0.045361220836639404, 1.4356510500811853e-14, 0.0879683569073677, 0.1926668882369995, 0.11698730289936066, 0.10425340384244919, 0.10466531664133072, 0.00027703188243322074, 1.1096164643316277e-14, 0.09124473482370377, 0.1122630387544632, 0.09372810274362564, 1.3490659869601351e-14, 0.03343462571501732, 8.246032607011223e-15, 1.458405743176225e-14, 0.0015662312507629395, 0.22066354751586914, 0.21067559719085693, 0.030831826850771904, 0.13225136697292328, 6.952621343366905e-15, 8.459843204655995e-15, 1.291244299255357e-14, 8.724356347490463e-15, 0.21163569390773773, 0.27076151967048645, 5.481462756840114e-15, 0.19130675494670868, 0.10302183032035828, 0.23687076568603516, 0.1996319591999054, 0.11800054460763931, 0.09292024374008179, 0.006930738687515259, 0.2118043154478073, 0.10951069742441177, 0.11600380390882492, 0.10753053426742554, 0.09820100665092468, 0.11273666471242905, 0.23157088458538055, 7.712934633964837e-15, 0.10343881696462631, 0.09439721703529358, 0.19852979481220245, 0.3030913472175598, 0.22887206077575684, 0.17433786392211914, 0.1927349865436554, 0.07909123599529266, 3.823711449513212e-05, 0.00943637266755104, 0.02951226569712162, 0.11042749136686325, 0.14785735309123993, 0.07718826830387115, 0.08513538539409637, 0.2235470861196518, 0.2364259511232376, 0.19261284172534943, 0.11221572756767273, 0.19583876430988312, 0.11837895959615707, 0.06706468015909195, 0.18589042127132416, 8.898982353962304e-15, 0.014840926043689251, 0.09754327684640884, 0.211390420794487, 0.32281792163848877, 1.4318075533797242e-14, 0.21909239888191223, 0.2343318909406662, 0.08278373628854752, 0.11641591787338257, 0.10584665834903717, 0.1148054227232933, 0.09413355588912964, 0.34496214985847473, 0.31385576725006104, 0.11508101224899292, 0.2982358932495117, 0.07091525197029114, 8.080311457913866e-15, 0.09734781086444855, 1.4595787144015826e-14, 0.009806418791413307, 0.2524418532848358, 0.010774207301437855, 0.09575004130601883, 9.522588338521654e-15, 0.10840663313865662, 0.15631265938282013, 0.1952359676361084, 0.21342995762825012, 0.11415877938270569, 0.11795508861541748, 0.06156817451119423, 0.29534977674484253, 0.09987358003854752, 0.22786572575569153, 0.0820002630352974, 0.13270391523838043, 0.08546314388513565, 0.09015285223722458, 0.0962221771478653, 0.33374595642089844, 0.0934184342622757, 0.07135569304227829, 0.147548645734787, 0.1081877127289772, 1.3825862994081874e-14, 0.22216109931468964, 0.17221300303936005, 0.05954102799296379, 0.10031333565711975, 1.4285203879180197e-14, 0.21446090936660767, 0.09144265949726105, 0.2120528221130371, 0.35321488976478577, 1.0855072808506339e-14, 0.10687917470932007, 0.11015800386667252, 5.6753646920926215e-15, 0.3778409957885742, 0.17145255208015442, 9.519793976828662e-15, 0.10810712724924088, 0.03593914955854416, 0.09425269812345505, 0.11081691831350327, 0.07564584910869598, 0.10326748341321945, 0.12832461297512054, 7.188139277867437e-15, 0.10978870838880539, 0.340665727853775, 8.47022274639165e-15, 0.006664578802883625, 0.09781304746866226, 0.20564886927604675, 0.22648689150810242, 0.10977428406476974, 1.082924507987866e-14, 0.22469361126422882, 0.42615237832069397, 0.11101414263248444, 0.06792787462472916, 0.0917169377207756, 0.0877138152718544, 0.11332198232412338, 1.1665439393539895e-14, 0.2268630564212799, 0.011674098670482635, 9.690242416804645e-15, 0.08827312290668488, 0.34612607955932617, 0.11126046627759933, 0.04155195504426956, 0.07740893959999084, 0.22058264911174774, 0.108614481985569, 0.07017239183187485, 0.08830925077199936, 0.2130332738161087, 0.08149133622646332, 0.10100460797548294, 0.1042424738407135, 0.056401535868644714, 0.24109862744808197, 0.09092873334884644, 0.1069130077958107, 0.10206260532140732, 0.18998222053050995, 1.2897691913777137e-14, 0.09508732706308365, 0.21923770010471344, 0.08020824939012527, 0.07964028418064117, 0.08852588385343552, 0.09162165224552155, 0.17222705483436584, 0.26638999581336975, 0.06239871680736542, 6.397434445122021e-15, 0.1354811191558838, 0.07171934843063354, 0.13182809948921204, 0.11597880721092224, 0.09119304269552231, 0.11486176401376724, 0.19949942827224731, 0.0036344644613564014, 1.3518877925206181e-14, 0.1033843383193016, 0.11622688919305801, 0.33554643392562866, 0.2171074002981186, 0.159244567155838, 0.11443134397268295, 0.045612066984176636, 0.09180028736591339, 0.08124362677335739, 0.11255395412445068, 0.10704770684242249, 0.10177282243967056, 0.23562176525592804, 0.27882325649261475, 4.039511136884073e-15, 0.1598874181509018, 3.863168194628147e-15, 0.19465439021587372, 0.11562648415565491, 0.10697388648986816, 0.3304820954799652, 0.35110267996788025, 0.10415288805961609, 0.12041600048542023, 0.21153892576694489, 1.3992310897447974e-14, 0.09929273277521133, 1.2663639769791828e-14, 0.11039324849843979, 0.15460574626922607, 0.11435084789991379, 1.1203072059721032e-14, 9.598236004007988e-15, 0.09571986645460129, 1.3488107759331274e-14, 0.2663893401622772, 0.05567731708288193, 0.10390303283929825, 0.3438345789909363, 0.2133912593126297, 0.21986597776412964, 0.23084548115730286, 1.080440837979927e-14, 0.10083887726068497, 0.2502083480358124, 7.358110565292009e-07, 0.09246547520160675, 5.958511712733736e-15, 0.001050853868946433, 0.11572171747684479, 7.993919179491611e-15, 0.07704336196184158, 0.08994020521640778, 0.21380086243152618, 0.10082229226827621, 1.1278670597296425e-14, 0.08585628122091293, 0.1983693242073059, 0.08189287036657333, 0.22099927067756653, 0.09112510830163956, 0.225224569439888, 0.07982291281223297, 0.04685723036527634, 0.0186079703271389, 0.10390225797891617, 5.960701716418862e-15, 1.1207525758957695e-14, 0.08709531277418137, 0.1039547547698021, 0.1553109586238861, 0.1003933846950531, 1.241991959174656e-14, 0.1062927320599556, 0.08851233869791031, 0.15978090465068817, 0.09687472134828568, 0.23420344293117523, 0.2643865644931793, 0.10075709968805313, 1.4465521947057587e-14, 0.11259543895721436, 0.03365153446793556, 0.20250304043293, 0.014265209436416626, 0.193923681974411, 8.44523781554649e-15, 0.09529876708984375, 0.03984517231583595, 0.09732948243618011, 0.2347346842288971, 0.10260970890522003, 0.4752439856529236, 0.2720281481742859, 0.07893599569797516, 0.0923939049243927, 9.627096110586836e-15, 8.656815634342299e-15, 9.377777891793164e-15, 0.09247986227273941, 0.2145034670829773, 0.07679691910743713, 6.6737916496579456e-15, 0.11365453153848648, 8.748894044939472e-15, 6.764833927154541, 3.482088565826416, 19.99304962158203, 11.61118221282959, 12.08489990234375, 3.167865514755249, 8.083660125732422, 7.606354713439941, 4.016745090484619, 12.408309936523438, 3.2262802124023438, 6.1406097412109375, 11.569580078125, 5.359920501708984, 7.91851806640625, 9.91505241394043, 5.005226135253906, 8.711621284484863, 5.903266429901123, 5.402259349822998, 7.0275092124938965, 6.3624267578125, 5.847099304199219, 5.110376834869385, 8.740753173828125, 6.7234344482421875, 3.9564924240112305, 18.848125457763672, 11.780829429626465, 5.234179973602295, 7.0980377197265625, 14.536117553710938, 4.092681884765625, 11.797700881958008, 7.400007724761963, 17.484025955200195, 8.05278491973877, 7.944053649902344, 6.288627624511719, 3.7403111457824707, 6.8157501220703125, 19.910980224609375, 18.351356506347656, 10.59816837310791, 10.303083419799805, 13.065985679626465, 6.833457946777344, 0.0, 8.4254150390625, 8.50053596496582, 10.0480318069458, 6.997949600219727, 20.294151306152344, 19.245407104492188, 13.33773422241211, 6.7145538330078125, 12.346564292907715, 9.706177711486816, 19.562408447265625, 29.815475463867188, 23.045623779296875, 10.922592163085938, 5.22015380859375, 5.781585693359375, 9.652725219726562, 12.460432052612305, 7.381235122680664, 8.690093994140625, 2.85952091217041, 4.253786087036133, 14.248710632324219, 7.750464916229248, 7.369884490966797, 16.280717849731445, 16.372562408447266, 16.734405517578125, 22.495996475219727, 5.036327838897705, 13.693992614746094, 11.270190238952637, 6.989264965057373, 6.018024921417236, 6.000943660736084, 9.462478637695312, 5.197495460510254, 14.245683670043945, 4.2858147621154785, 19.167009353637695, 23.748929977416992, 24.445547103881836, 6.428579330444336, 2.5961644649505615, 6.334211349487305, 13.433734893798828, 5.909299373626709, 3.2989501953125, 8.20645809173584, 12.347579956054688, 3.1455001831054688, 8.016632080078125, 12.368700981140137, 2.4333648681640625, 22.73215103149414, 5.338372707366943, 11.629905700683594, 25.316207885742188, 7.3486785888671875, 6.1310577392578125, 8.906288146972656, 14.324028015136719, 13.486653327941895, 9.194290161132812, 12.963109016418457, 8.319952964782715, 36.53587341308594, 2.9658610820770264, 19.313705444335938, 4.136177062988281, 8.034505844116211, 3.865969657897949, 13.537956237792969, 3.3500595092773438, 31.903732299804688, 9.37916088104248, 5.017234802246094, 9.182099342346191, 20.02071762084961, 20.414588928222656, 8.91464900970459, 7.967247009277344, 7.274229049682617, 5.873769283294678, 5.105233192443848, 11.67802906036377, 11.064406394958496, 19.881120681762695, 6.13116455078125, 5.164054870605469, 11.071748733520508, 4.1790771484375, 24.65506362915039, 3.9781129360198975, 5.084527492523193, 4.677848815917969, 25.06270408630371, 8.248748779296875, 12.057235717773438, 12.908309936523438, 6.362854957580566, 6.162384033203125, 14.929340362548828, 5.649966716766357, 11.676475524902344, 19.33270263671875, 6.7080841064453125, 8.283599853515625, 20.15467071533203, 7.421890735626221, 36.48048400878906, 35.98345947265625, 13.9354248046875, 5.082550048828125, 5.8212127685546875, 17.06513786315918, 8.65916919708252, 20.834518432617188, 10.286117553710938, 11.283256530761719, 10.07480525970459, 14.81542682647705, 4.045961380004883, 6.797996520996094, 42.66997146606445, 7.496253490447998, 16.77013397216797, 7.530933856964111, 4.171189308166504, 17.537757873535156, 4.763526916503906, 6.284328460693359, 5.44301700592041, 10.200958251953125, 4.363067626953125, 6.055049419403076, 20.107650756835938, 2.879202127456665, 12.128402709960938, 9.480030059814453, 28.25244140625, 6.129539489746094, 5.1633453369140625, 4.067668914794922, 31.962753295898438, 16.865631103515625, 5.161812782287598, 9.819734573364258, 7.755437850952148, 5.35748291015625, 28.164037704467773, 13.348981857299805, 2.1137237548828125, 9.36927318572998, 7.889014720916748, 7.5496063232421875, 3.9745025634765625, 19.4180908203125, 12.913393020629883, 16.810882568359375, 6.8470001220703125, 4.074951648712158, 5.390505790710449, 10.917999267578125, 7.03312873840332, 17.00250244140625, 34.811073303222656, 13.904045104980469, 4.46242618560791, 4.856086730957031, 5.050285339355469, 7.827545166015625, 9.218948364257812, 6.6392388343811035, 27.514938354492188, 15.666015625, 4.56938362121582, 10.975189208984375, 8.850944519042969, 0.8932723999023438, 2.999406576156616, 7.4637908935546875, 2.095123291015625, 10.147732734680176, 8.483380317687988, 3.1642467975616455, 44.70986557006836, 3.23822021484375, 31.84211540222168, 14.927047729492188, 7.918361663818359, 26.688766479492188, 23.39508819580078, 5.938697338104248, 22.620208740234375, 4.053596019744873, 5.4460344314575195, 11.690260887145996, 9.61931037902832, 15.130812644958496, 10.689048767089844, 17.363332748413086, 10.210662841796875, 4.623486042022705, 11.0889253616333, 2.3736724853515625, 7.176694393157959, 5.438838958740234, 12.35678768157959, 7.601986408233643, 8.5250244140625, 28.104270935058594, 15.72042465209961, 7.909005165100098, 6.513275146484375, 5.152153015136719, 9.595255851745605, 14.497833251953125, 7.074577331542969, 6.956085205078125, 6.168914794921875, 5.066734313964844, 12.2406005859375, 11.186063766479492, 12.30202579498291, 12.976615905761719, 8.676739692687988, 17.718442916870117, 6.2519378662109375, 24.310470581054688, 3.3946990966796875, 3.7309911251068115, 27.767745971679688, 4.657824993133545, 3.889694929122925, 4.058525085449219, 6.138948917388916, 7.0591278076171875, 5.046290874481201, 5.992734432220459, 6.118812084197998, 18.77815055847168, 5.946497440338135, 5.68841552734375, 5.306525707244873, 6.94700813293457, 23.074554443359375, 47.05166244506836, 13.007492065429688, 6.083244323730469, 3.949035882949829, 5.393006324768066, 2.3765344619750977, 0.15281963348388672, 1.57835853099823, 2.186012029647827, 1.677048921585083, 0.7474195957183838, 1.1951017379760742, 1.420021891593933, 0.033726826310157776, 1.0501012802124023, 1.1394262313842773, 0.6772974133491516, 1.1962385177612305, 2.844464063644409, 9.5367431640625e-07, 0.2188340723514557, 2.323719024658203, 0.8501479625701904, 1.33076012134552, 9.5367431640625e-07, 1.7909914255142212, 0.6347074508666992, 1.9707119464874268, 1.1745574474334717, 2.607828378677368, 2.1095972061157227, 2.548182725906372, 2.0679702758789062, 1.5699340105056763, 1.7315865755081177, 1.4034394025802612, 3.090264320373535, 1.249936580657959, 0.8826572895050049, 0.07488727569580078, 2.4533989429473877, 1.3140478134155273, 1.4011547565460205, 9.5367431640625e-07, 2.36488676071167, 2.0215988159179688, 1.3760613203048706, 2.0035924911499023, 0.7230271697044373, 1.2318947315216064, 1.6180143356323242, 2.215583086013794, 0.009582576341927052, 0.8558360934257507, 1.9390093088150024, 1.8746856451034546, 2.6436619758605957, 0.2690134048461914, 1.5545583963394165, 1.7098596096038818, 2.699511766433716, 1.5188781023025513, 1.8450781106948853, 1.2819684743881226, 2.0018746852874756, 2.0723657608032227, 9.5367431640625e-07, 0.9112405180931091, 2.319843292236328, 2.171375036239624, 1.6545380353927612, 9.5367431640625e-07, 1.4394116401672363, 1.8868012428283691, 1.7201446294784546, 1.2133030891418457, 1.7313745021820068, 1.8983538150787354, 0.2519904673099518, 0.8476859927177429, 1.396803855895996, 1.769824504852295, 1.36546790599823, 1.1391199827194214, 1.9598397016525269, 1.4460265636444092, 1.515467643737793, 1.4940422773361206, 2.0715951919555664, 1.5900123119354248, 1.7978469133377075, 2.0065624713897705, 2.058596611022949, 1.662872314453125, 1.5243014097213745, 1.2144478559494019, 1.4328043460845947, 2.1816840171813965, 1.261138916015625, 1.3202123641967773, 0.42617130279541016, 1.115883708000183, 1.0146225690841675, 1.658303141593933, 1.590757966041565, 2.0092597007751465, 1.8255661725997925, 0.839961051940918, 0.07424640655517578, 1.6591540575027466, 1.7075964212417603, 2.2205357551574707, 0.06499581784009933, 1.3072195053100586, 1.5609170198440552, 1.5556045770645142, 2.641443967819214, 0.09443000704050064, 1.7889374494552612, 9.5367431640625e-07, 2.5325028896331787, 1.4905999898910522, 1.62852144241333, 1.9486138820648193, 9.5367431640625e-07, 2.305159568786621, 1.585524559020996, 2.074613571166992, 1.2486257553100586, 0.925628662109375, 1.2506760358810425, 1.64189612865448, 9.5367431640625e-07, 1.7404851913452148, 2.3618032932281494, 2.0226857662200928, 1.7062945365905762, 2.0962705612182617, 1.9146642684936523, 9.5367431640625e-07, 1.4771088361740112, 1.3120815753936768, 0.936897337436676, 1.2583855390548706, 2.3067476749420166, 1.2559795379638672, 1.5912742614746094, 0.2193080633878708, 0.7176772952079773, 1.7120941877365112, 1.8178085088729858, 1.645015835762024, 1.565306544303894, 1.5005425214767456, 1.3866338729858398, 2.1134767532348633, 1.7118122577667236, 1.6924009323120117, 2.3268353939056396, 1.377156138420105, 1.5109084844589233, 2.4695160388946533, 0.9371575713157654, 1.7164123058319092, 1.0512465238571167, 9.5367431640625e-07, 9.5367431640625e-07, 1.4646410942077637, 1.9143441915512085, 1.574538230895996, 2.6087050437927246, 1.1739815473556519, 1.6594728231430054, 1.3630231618881226, 1.5311614274978638, 1.5853089094161987, 1.502004623413086, 0.88251793384552, 1.3574895858764648, 1.9449560642242432, 1.6104388236999512, 2.336353302001953, 1.6916321516036987, 1.8072068691253662, 1.365593433380127, 1.3751572370529175, 9.5367431640625e-07, 0.06304073333740234, 3.0533885955810547, 0.7910780906677246, 2.307736396789551, 1.89836585521698, 2.3394219875335693, 1.843188762664795, 1.079595923423767, 1.4994176626205444, 1.6044548749923706, 1.041884422302246, 1.1752004623413086, 1.2383354902267456, 2.192093849182129, 1.9100884199142456, 1.3297309875488281, 1.521906852722168, 0.9604177474975586, 1.2505100965499878, 1.0736303329467773, 1.0194730758666992, 1.638224720954895, 2.576795816421509, 0.11683845520019531, 1.5388123989105225, 1.1012879610061646, 2.271350860595703, 9.5367431640625e-07, 1.7998793125152588, 1.1548393964767456, 1.2275017499923706, 9.5367431640625e-07, 1.1138262748718262, 2.1197619438171387, 1.5847203731536865, 1.0539052486419678, 2.7939770221710205, 1.796096920967102, 2.6014089584350586, 1.990960955619812, 1.357519507408142, 1.5146764516830444, 1.7561653852462769, 2.0516059398651123, 1.0203839540481567, 1.5383881330490112, 1.4954092502593994, 1.1152313947677612, 1.8729158639907837, 1.4687707424163818, 0.6599863171577454, 1.4355878829956055, 9.5367431640625e-07, 0.6396017074584961, 1.2758946418762207, 2.3627285957336426, 1.1380647420883179, 1.4254696369171143, 1.6594371795654297, 2.1637988090515137, 1.5919926166534424, 1.3748444318771362, 1.1027493476867676, 9.5367431640625e-07, 1.9886054992675781, 1.351393699645996, 0.8675651550292969, 0.5127592086791992, 1.3926312923431396, 2.7643327713012695, 2.513132333755493, 2.1234848499298096, 9.5367431640625e-07, 1.3497310876846313, 1.368782639503479, 1.6134123802185059, 9.5367431640625e-07, 2.11185359954834, 1.4808586835861206, 1.0212355852127075, 1.333339810371399, 9.5367431640625e-07, 0.9415148496627808, 1.3904045820236206, 0.7019939422607422, 1.3098877668380737, 1.5032925605773926, 0.16443347930908203, 1.8831212520599365, 1.2139527797698975, 1.7873684167861938, 0.6896839737892151, 0.41228771209716797, 1.5635842084884644, 2.05401611328125, 2.0098135471343994, 1.9512685537338257, 2.554616689682007, 1.7845333814620972, 2.0280351638793945, 1.3551913499832153, 0.4302988052368164, 9.5367431640625e-07, 1.2539364099502563, 1.1712446212768555, 2.0710813999176025, 2.0204665660858154, 2.2581264972686768, 9.5367431640625e-07, 9.5367431640625e-07, 0.9589542746543884, 0.8719282150268555, 2.943180799484253, 1.8766976594924927, 1.6535273790359497, 1.7322628498077393, 1.0549105405807495, 2.2647151947021484, 0.0, 0.008459395729005337, 0.0019857287406921387, 0.002700344193726778, 0.029075998812913895, 0.0002946650783997029, 0.0498347282409668, 0.0027359197847545147, 0.001169620081782341, 0.0009352314518764615, 0.0, 0.0065193758346140385, 1.1627674211922567e-05, 0.038922786712646484, 0.062101658433675766, 0.0, 0.03458073362708092, 0.0011924022110179067, 0.0, 2.4635790396132506e-05, 0.05899067595601082, 0.0, 0.0, 0.019757764413952827, 0.0010842084884643555, 0.01153020840138197, 0.0, 0.007141292095184326, 0.062101658433675766, 0.00146761117503047, 0.007148855831474066, 0.00037898955633863807, 0.0012212449219077826, 0.0, 0.045636728405952454, 0.041628122329711914, 0.0, 0.00380929047241807, 2.5095938326558098e-05, 0.0007031565764918923, 0.0, 5.9604643443123e-10, 0.029125746339559555, 0.0035266822669655085, 0.08086872100830078, 0.0, 0.04396390914916992, 0.0019298207480460405, 0.0, 5.9604643443123e-10, 0.012712300755083561, 0.02849799394607544, 0.0166249331086874, 0.05014997720718384, 0.07051443308591843, 0.019391058012843132, 0.06687314808368683, 0.05529302358627319, 0.005820310674607754, 0.0, 0.001131892204284668, 0.06692724674940109, 0.000982046127319336, 0.004871919751167297, 0.058367472141981125, 0.02177819050848484, 0.02493879199028015, 8.350610301022243e-07, 0.04656863212585449, 0.0, 0.001605265075340867, 0.06705266982316971, 0.0, 0.0231635645031929, 0.0008794653113000095, 0.0, 0.000632941722869873, 0.0161325354129076, 0.0036024642176926136, 0.0006476688431575894, 0.00011144220479764044, 0.0, 0.05106675997376442, 0.0, 0.03671795129776001, 0.01006200723350048, 0.0, 1.7881393032936899e-09, 0.0007266789325512946, 0.0, 0.009914638474583626, 0.02676037698984146, 0.0010817628353834152, 0.03673761337995529, 0.0, 0.0030982494354248047, 3.457069396972656e-05, 0.055831488221883774, 0.03368955850601196, 0.014664532616734505, 0.031899407505989075, 0.08941119909286499, 0.002497998997569084, 0.004370579030364752, 0.003652213839814067, 0.0, 0.04850506782531738, 0.0004309916403144598, 1.1563301086425781e-05, 0.0, 2.05278388420993e-06, 0.009755909442901611, 5.9604643443123e-10, 0.02633790485560894, 2.3847817374189617e-06, 0.0, 0.057148225605487823, 0.061572227627038956, 0.05218414217233658, 0.0, 0.0081881582736969, 0.045361220836639404, 0.0, 0.04619128629565239, 0.0, 0.0023053300101310015, 9.751319885253906e-05, 0.04162812978029251, 0.0007910931017249823, 0.007254960481077433, 0.002788720652461052, 1.9550323486328125e-05, 0.0, 0.006557179149240255, 0.0, 0.0006871819496154785, 0.018134955316781998, 0.02414870634675026, 0.0016027664532884955, 0.0, 0.0023927700240164995, 0.04162992537021637, 0.0015160118928179145, 0.012530539184808731, 0.005702749826014042, 0.0007913362933322787, 0.0013868289534002542, 0.045361220836639404, 0.015935780480504036, 0.0, 0.0, 0.0006364834262058139, 0.006342890206724405, 0.01238467637449503, 0.0, 0.0, 0.0032380903139710426, 0.0, 0.00414663553237915, 0.03403020650148392, 0.013516237027943134, 0.007187135051935911, 0.0, 0.006251083686947823, 0.0029369592666625977, 0.0, 0.0708322525024414, 4.6744346036575735e-05, 0.002070009708404541, 0.0, 0.0, 0.012668387964367867, 0.009248385205864906, 1.7881393032936899e-09, 0.01654505729675293, 1.2242793445693678e-06, 0.00016117095947265625, 0.04633751139044762, 0.01563512533903122, 0.004361271858215332, 0.040870122611522675, 0.05529302358627319, 9.031831723405048e-05, 0.0139014208689332, 0.0, 0.07970774173736572, 0.0, 3.823638053290779e-06, 0.041628122329711914, 0.03864210844039917, 0.00035828351974487305, 0.0, 0.015307256951928139, 0.0, 5.9604643443123e-10, 0.06387174129486084, 0.0007026773528195918, 0.0026648950297385454, 0.041628122329711914, 0.0, 0.01632779836654663, 0.0031669079326093197, 0.0005703115602955222, 0.06859643012285233, 0.0022139863576740026, 0.041628122329711914, 0.0, 3.397464638510428e-07, 9.500980377197266e-05, 0.0044096666388213634, 0.041628122329711914, 0.045641716569662094, 0.009472868405282497, 0.0, 0.0708322525024414, 0.0007693016086705029, 0.0, 0.0, 0.0, 3.982126509072259e-05, 0.005864629056304693, 0.05938045680522919, 0.0, 0.009118333458900452, 0.03791791945695877, 0.041628122329711914, 2.2637843358097598e-05, 1.19209286886246e-09, 0.0, 0.0, 0.0, 0.006054927594959736, 0.0, 0.0028715645894408226, 0.0, 0.0, 0.0, 0.006591379642486572, 0.0, 0.018128395080566406, 0.0036002355627715588, 0.002554600825533271, 0.011666953563690186, 2.2470951080322266e-05, 0.045999955385923386, 0.0, 0.020432857796549797, 0.0, 0.0, 0.0, 0.0008136790711432695, 0.04387602582573891, 0.020335718989372253, 0.002620953368023038, 0.0, 0.0, 0.01279708556830883, 0.0018909000791609287, 0.03030341863632202, 0.0, 0.0, 0.0, 0.0, 0.0, 0.002009665360674262, 0.0007257562829181552, 0.0, 0.010350534692406654, 0.0, 0.0, 0.0, 0.0, 0.0018039947608485818, 0.00045340537326410413, 0.01582765020430088, 0.006533085368573666, 0.03224330022931099, 0.0013508200645446777, 0.08792241662740707, 8.505582809448242e-05, 0.001459956169128418, 0.0, 0.022090358659625053, 0.004017424304038286, 9.073614819499198e-06, 0.001675159321166575, 0.05105763301253319, 0.0, 0.0, 0.0, 0.01585189439356327, 0.04162883758544922, 0.0, 0.0044306376948952675, 0.0, 0.0, 0.0, 0.03609825670719147, 0.0, 0.0, 9.253973015123634e-15, 0.08826453983783722, 0.1766282618045807, 0.1363232135772705, 0.1325218826532364, 0.18747146427631378, 0.02185741439461708, 0.08106912672519684, 0.1426052451133728, 0.08399084210395813, 0.06482589244842529, 0.16671477258205414, 9.79054467028671e-15, 0.22775378823280334, 0.09792014211416245, 0.19298717379570007, 0.1470007300376892, 0.23204675316810608, 0.03322194516658783, 0.08919664472341537, 0.19408614933490753, 0.09542008489370346, 0.10658065229654312, 0.0874641090631485, 1.332300579131836e-14, 0.020085854455828667, 0.0717071071267128, 1.0967639252031699e-14, 1.2144497511584404e-14, 0.20068252086639404, 0.10930410027503967, 0.20122814178466797, 0.0976707711815834, 0.2454511970281601, 0.09649615734815598, 1.1434821968155703e-14, 0.1423650085926056, 0.0008380965446121991, 0.09424708038568497, 0.21118541061878204, 0.09053287655115128, 0.2115420550107956, 0.2817111015319824, 0.300486296415329, 0.19872723519802094, 0.28089916706085205, 0.10407761484384537, 0.19794686138629913, 0.08931293338537216, 0.07815144211053848, 1.504038457363424e-14, 0.07917376607656479, 0.09621436893939972, 0.031659048050642014, 0.08423519134521484, 0.09776708483695984, 0.11256164312362671, 0.20419399440288544, 0.08156399428844452, 0.14235246181488037, 1.482130797215639e-14, 0.2194872945547104, 0.3559638559818268, 0.2081657499074936, 8.925580035539036e-15, 0.09977699816226959, 9.174821174334508e-15, 0.31726136803627014, 0.0017490958562120795, 0.08643827587366104, 0.08154573291540146, 0.14291152358055115, 0.46227797865867615, 0.07686735689640045, 0.09869470447301865, 0.12234876304864883, 0.0007146552088670433, 0.0035239718854427338, 0.08134649693965912, 0.0007104897522367537, 0.26125237345695496, 0.23235686123371124, 0.22862417995929718, 0.09903669357299805, 1.1402094309139691e-14, 0.1632704734802246, 0.034765299409627914, 0.10854707658290863, 0.2571640610694885, 0.09184381365776062, 0.16442063450813293, 0.0024825935252010822, 0.19587142765522003, 0.10079757124185562, 0.26975664496421814, 0.19924049079418182, 0.15351414680480957, 0.09371665865182877, 0.10463138669729233, 0.10324248671531677, 0.1786523163318634, 0.11192373186349869, 0.1619105041027069, 0.0470002219080925, 4.782960848535118e-15, 0.1826746016740799, 0.30374854803085327, 0.10214933007955551, 0.3437008559703827, 0.04084865003824234, 0.10910061001777649, 0.19513551890850067, 0.21189315617084503, 1.006149526352031e-14, 0.33276134729385376, 8.982443978311494e-05, 0.10570903867483139, 0.2020101547241211, 0.09223850071430206, 0.09124742448329926, 1.481905825264848e-14, 0.05739534646272659, 0.09380096197128296, 0.09363136440515518, 4.717463178855732e-15, 0.031878527253866196, 0.231169655919075, 0.08008960634469986, 5.547114162999427e-15, 0.13795016705989838, 0.10927385091781616, 0.08656168729066849, 9.599116918273132e-15, 0.10651597380638123, 7.924430290564763e-15, 0.09411483258008957, 0.1658075451850891, 0.3365841507911682, 8.321828503263327e-15, 0.1065036728978157, 0.1013621911406517, 0.11895717680454254, 0.10905452817678452, 0.11646340042352676, 0.16886277496814728, 0.1789582073688507, 0.017155740410089493, 1.3577929674156962e-14, 0.1045353040099144, 7.7204732271954e-15, 0.0990995541214943, 0.2319798469543457, 0.09324565529823303, 0.11146733909845352, 0.3132520020008087, 0.1094873696565628, 0.22162692248821259, 0.004772636108100414, 0.06385986506938934, 3.429142088862136e-05, 0.1147226095199585, 0.2159021645784378, 0.03298860043287277, 0.2395077496767044, 0.3342542052268982, 5.711854447943863e-15, 0.12969976663589478, 0.2415681928396225, 0.021766528487205505, 0.07924401760101318, 0.3268607258796692, 0.2179327756166458, 7.629951142007485e-05, 0.10739296674728394, 0.025670954957604408, 0.10855735838413239, 0.06616657227277756, 0.2277555763721466, 0.2291947454214096, 0.10093793272972107, 0.09248939901590347, 0.23334646224975586, 0.001175370067358017, 7.473182805277454e-15, 0.08733794838190079, 0.16003039479255676, 8.578650586936725e-15, 0.35348159074783325, 8.74920660009701e-15, 0.1630585789680481, 0.23307225108146667, 0.09076803177595139, 0.02628404274582863, 0.09936002641916275, 0.22393086552619934, 0.20274718105793, 0.04327436536550522, 0.15145684778690338, 0.11520377546548843, 0.07957153022289276, 0.09392940998077393, 0.20249703526496887, 0.0960773229598999, 0.07671676576137543, 6.779717778393306e-15, 0.1042267456650734, 0.31686532497406006, 0.14048729836940765, 0.08896533399820328, 0.09343230724334717, 0.08388878405094147, 0.10628807544708252, 0.09795469045639038, 0.32217222452163696, 0.07787079364061356, 0.10407127439975739, 3.257237403886393e-05, 5.157988921096696e-15, 0.15595659613609314, 0.3460024297237396, 0.22797837853431702, 0.001098928856663406, 0.10236497968435287, 0.09472902119159698, 0.022805413231253624, 7.512420759526062e-15, 0.09877458959817886, 0.21931250393390656, 0.10936792194843292, 0.11622408777475357, 0.3056740164756775, 0.08654482662677765, 0.3731345236301422, 0.08974681794643402, 1.199869180114289e-14, 6.3827845867827845e-15, 0.12927043437957764, 0.22579677402973175, 1.1890867895089207e-14, 0.12989108264446259, 0.08981171995401382, 0.10795757174491882, 0.08770684152841568, 0.22903187572956085, 0.07670478522777557, 7.92225934512095e-15, 0.2140529602766037, 0.025068610906600952, 0.10344699770212173, 0.23655173182487488, 0.09696725755929947, 0.0882299467921257, 0.07898733764886856, 0.11940380930900574, 6.750126682380977e-15, 0.22532592713832855, 0.27086153626441956, 0.11195870488882065, 0.30901026725769043, 0.10500741750001907, 0.23324722051620483, 0.08064025640487671, 0.16849970817565918, 0.11116161197423935, 0.09884876012802124, 0.008784869685769081, 0.13733401894569397, 0.1126294881105423, 5.3937339544063434e-05, 0.13279421627521515, 0.09208837151527405, 0.16978685557842255, 0.1957785189151764, 0.1030510663986206, 0.18839366734027863, 0.05196812376379967, 0.12908479571342468, 0.20712488889694214, 0.1134164109826088, 0.22468215227127075, 0.0943112000823021, 0.14825953543186188, 0.0826408639550209, 0.23450641334056854, 0.016357749700546265, 6.7097562450818896e-15, 0.2176152765750885, 0.19110722839832306, 0.09163398295640945, 0.08272822201251984, 0.08983025699853897, 1.3762723464127644e-14, 0.2148163616657257, 0.11788582801818848, 0.12448093295097351, 0.2583993673324585, 0.16143301129341125, 0.11079009622335434, 0.2006159871816635, 5.8143691514841566e-15, 5.080821990966797, 5.992741107940674, 17.301803588867188, 14.846176147460938, 8.701416015625, 0.0, 5.316886901855469, 10.026251792907715, 10.113822937011719, 9.050995826721191, 5.265379428863525, 14.115631103515625, 11.076796531677246, 5.115312576293945, 19.327621459960938, 16.968997955322266, 16.29261589050293, 11.8941650390625, 11.981457710266113, 8.7674560546875, 6.9954833984375, 19.030372619628906, 4.805572509765625, 10.084136962890625, 12.005267143249512, 4.3528900146484375, 21.45430564880371, 9.452492713928223, 10.037848472595215, 7.450812816619873, 9.061983108520508, 13.532607078552246, 28.60614776611328, 7.917751312255859, 4.276924133300781, 12.165021896362305, 9.718460083007812, 9.884174346923828, 3.2979812622070312, 11.873613357543945, 12.959991455078125, 19.767333984375, 12.892744064331055, 16.47869110107422, 4.993209362030029, 6.17485237121582, 17.640798568725586, 16.17262077331543, 14.201056480407715, 5.127778053283691, 8.176017761230469, 10.880541801452637, 3.6645965576171875, 4.650169372558594, 28.23347282409668, 7.193840026855469, 21.277456283569336, 5.2921905517578125, 8.023408889770508, 9.650985717773438, 14.108527183532715, 7.296040058135986, 23.152212142944336, 6.03433084487915, 16.813051223754883, 21.984149932861328, 8.400816917419434, 7.432535171508789, 9.44749641418457, 5.948657512664795, 12.828577995300293, 5.104209899902344, 12.578269958496094, 8.312850952148438, 1.7547606603329768e-06, 22.666351318359375, 10.804699897766113, 16.096405029296875, 42.3885498046875, 7.082611083984375, 11.61557674407959, 8.251917839050293, 6.881324291229248, 9.578635215759277, 7.254233360290527, 8.63821792602539, 13.208598136901855, 3.053955078125, 7.523226737976074, 2.676668882369995, 22.87904167175293, 17.528587341308594, 5.1832427978515625, 16.776254653930664, 3.282501220703125, 5.8857269287109375, 4.5564775466918945, 4.01844596862793, 11.756332397460938, 6.1422119140625, 32.93811798095703, 9.5224609375, 8.235613822937012, 5.034788131713867, 18.42896270751953, 5.479442119598389, 5.0196003913879395, 22.90119171142578, 6.703216552734375, 13.130268096923828, 5.304459571838379, 5.5947265625, 5.939478397369385, 11.188483238220215, 6.5542755126953125, 25.13018798828125, 6.129940032958984, 5.865478515625, 4.1168060302734375, 3.960026264190674, 12.20938491821289, 24.956567764282227, 4.98447322845459, 6.684967041015625, 11.82752513885498, 35.27882385253906, 3.0023040771484375, 9.831924438476562, 39.66719055175781, 10.565879821777344, 2.724916934967041, 4.9861741065979, 6.8918023109436035, 5.011474609375, 12.0181884765625, 7.040688991546631, 8.330169677734375, 3.9715816974639893, 7.576072692871094, 21.05022430419922, 6.725957870483398, 7.969751834869385, 4.04864501953125, 11.767929077148438, 7.281078338623047, 10.973663330078125, 6.736579418182373, 13.026312828063965, 37.06305694580078, 8.989127159118652, 6.4633941650390625, 13.098898887634277, 7.498176574707031, 13.574042320251465, 14.485857009887695, 7.561668395996094, 17.65838623046875, 33.07443618774414, 4.119163513183594, 7.065940856933594, 35.876312255859375, 34.51947021484375, 29.8577880859375, 26.646230697631836, 7.943634986877441, 6.943057537078857, 15.727736473083496, 8.803085327148438, 11.494929313659668, 11.050437927246094, 9.769740104675293, 6.4656829833984375, 11.12503719329834, 35.54150390625, 9.45789909362793, 35.27006530761719, 18.10991668701172, 17.39411735534668, 10.306828498840332, 7.077962398529053, 8.71225643157959, 14.284835815429688, 13.563278198242188, 11.627516746520996, 31.05122184753418, 6.602195739746094, 3.9698333740234375, 14.073504447937012, 9.113348960876465, 9.531486511230469, 10.863006591796875, 9.687018394470215, 20.497283935546875, 7.154480934143066, 11.843917846679688, 17.259366989135742, 5.000663757324219, 57.09239196777344, 4.8380279541015625, 16.50988006591797, 11.92247486114502, 4.263519287109375, 12.23435115814209, 15.600495338439941, 21.179941177368164, 29.21624755859375, 41.76682662963867, 29.46319007873535, 26.71735954284668, 5.726114273071289, 23.719467163085938, 17.17303466796875, 20.213165283203125, 24.321386337280273, 8.761354446411133, 8.0455322265625, 10.658453941345215, 6.911438941955566, 6.867368221282959, 7.97428035736084, 12.88700008392334, 9.231189727783203, 5.0199127197265625, 8.659561157226562, 9.281820297241211, 8.00119686126709, 13.707366943359375, 16.108436584472656, 12.363548278808594, 4.934779644012451, 34.93560791015625, 8.058013916015625, 20.04840850830078, 20.760848999023438, 5.119384765625, 10.97882080078125, 9.932394027709961, 9.039678573608398, 67.47154235839844, 9.462631225585938, 5.8496246337890625, 12.183258056640625, 8.563674926757812, 11.602508544921875, 26.59772491455078, 5.77537202835083, 10.292236328125, 11.10936164855957, 5.708871841430664, 16.71916961669922, 6.000091552734375, 7.5537943840026855, 24.174562454223633, 12.13003921508789, 7.8039093017578125, 9.41983699798584, 6.95550537109375, 5.300684928894043, 27.7372989654541, 6.053547382354736, 6.138476371765137, 26.710111618041992, 12.124674797058105, 27.94290542602539, 10.195579528808594, 6.0913848876953125, 39.36810302734375, 15.321884155273438, 20.170196533203125, 4.155212879180908, 9.304936408996582, 9.905197143554688, 7.76251220703125, 17.92426872253418, 12.847030639648438, 12.83892822265625, 12.9866943359375, 12.601210594177246, 17.14759635925293, 8.994308471679688, 8.190948486328125, 33.55963134765625, 8.256007194519043, 6.999284744262695, 15.397750854492188, 27.362274169921875, 3.613081932067871, 11.735487937927246, 21.656278610229492, 7.2580718994140625, 15.93450927734375, 17.35236930847168, 7.3486785888671875, 5.9833574295043945, 17.511472702026367, 15.595499992370605, 6.911094665527344, 6.525184154510498, 2.9870753288269043, 13.98583984375, 1.8487786054611206, 1.0680114030838013, 0.4679574966430664, 1.490230679512024, 9.5367431640625e-07, 2.3091039657592773, 2.028695821762085, 1.6598830223083496, 0.8931187391281128, 2.238705635070801, 0.8259801864624023, 1.3329648971557617, 2.0253453254699707, 1.2664178609848022, 1.4090551137924194, 1.839852213859558, 2.332711696624756, 0.07816600799560547, 2.530459403991699, 2.5900964736938477, 0.7938966155052185, 1.6972533464431763, 1.840294599533081, 1.2577691078186035, 0.07767391204833984, 9.5367431640625e-07, 2.4567832946777344, 2.111217975616455, 2.1013147830963135, 2.425381660461426, 1.839577555656433, 1.991817831993103, 1.2298791408538818, 1.9465683698654175, 0.41986510157585144, 0.016081923618912697, 0.5244532823562622, 1.2098040580749512, 2.2067601680755615, 1.5071172714233398, 2.2126333713531494, 2.0196452140808105, 1.6343814134597778, 0.4450540542602539, 1.275761604309082, 1.7444223165512085, 0.7251005172729492, 1.0536789894104004, 1.6352838277816772, 1.0356072187423706, 1.006966471672058, 1.25017249584198, 1.5257240533828735, 1.7830562591552734, 1.4420238733291626, 1.3334527015686035, 1.7075481414794922, 1.2393089532852173, 1.5192657709121704, 2.197138786315918, 1.5110464096069336, 1.3689184188842773, 1.0310906171798706, 1.4772387742996216, 1.605851411819458, 0.0022420883178710938, 9.5367431640625e-07, 9.5367431640625e-07, 1.4059921503067017, 1.8575280904769897, 1.461182951927185, 1.6889715194702148, 1.6817224025726318, 0.6669530868530273, 1.8273786306381226, 1.3852574825286865, 1.3653135299682617, 1.7479894161224365, 1.358809471130371, 1.219813346862793, 0.7693108916282654, 2.319578170776367, 9.5367431640625e-07, 1.2706639766693115, 1.8355873823165894, 1.5417447090148926, 1.740883708000183, 1.7352170944213867, 1.4879226684570312, 1.7690808773040771, 9.5367431640625e-07, 2.157278299331665, 1.3024320602416992, 1.20537269115448, 2.0797979831695557, 1.8191155195236206, 1.2924575805664062, 2.480203151702881, 0.8318948745727539, 2.0568859577178955, 1.91280198097229, 1.3299721479415894, 1.7868889570236206, 2.2834537029266357, 1.9511994123458862, 2.834752321243286, 1.0545822381973267, 2.2315664291381836, 1.762198805809021, 1.819416880607605, 1.8074684143066406, 1.3524622917175293, 1.1375442743301392, 1.6129567623138428, 2.1247901916503906, 1.2083710432052612, 1.507338523864746, 9.5367431640625e-07, 0.8032488822937012, 1.9073781967163086, 2.592257022857666, 2.3348376750946045, 1.3588045835494995, 1.619135856628418, 1.466410756111145, 1.6721209287643433, 1.8574590682983398, 2.396491527557373, 2.165205717086792, 1.843430757522583, 1.583510398864746, 2.55574631690979, 2.07106351852417, 1.1503390073776245, 9.5367431640625e-07, 1.540791392326355, 1.8248505592346191, 1.1575859785079956, 1.2373473644256592, 1.5774775743484497, 9.5367431640625e-07, 1.3746193647384644, 2.2039635181427, 0.7871589660644531, 0.8707191944122314, 2.4938323497772217, 1.504012107849121, 1.1860723495483398, 2.86929988861084, 1.931388258934021, 2.0202836990356445, 2.567244291305542, 1.4331939220428467, 1.1409119367599487, 2.1555774211883545, 0.9719048738479614, 1.8430635929107666, 0.9559681415557861, 1.7587913274765015, 2.3199586868286133, 2.2442450523376465, 9.5367431640625e-07, 1.6604927778244019, 1.541544795036316, 1.3099035024642944, 0.2562875747680664, 0.8338986039161682, 1.0357636213302612, 1.7388890981674194, 2.2974889278411865, 0.012818336486816406, 0.6525054574012756, 1.5247772932052612, 1.8665063381195068, 1.3023443222045898, 2.7111010551452637, 1.5323388576507568, 1.5068283081054688, 1.5022743940353394, 1.6370971202850342, 1.127711296081543, 0.826716423034668, 1.852620005607605, 1.5293282270431519, 1.093451976776123, 2.5088095664978027, 1.1758919954299927, 1.1426572799682617, 2.680546760559082, 9.5367431640625e-07, 0.7057105898857117, 0.5223531723022461, 1.599886417388916, 0.615993082523346, 1.7352733612060547, 1.4413193464279175, 1.8340078592300415, 0.45160579681396484, 0.1966887265443802, 1.8050801753997803, 1.3057584762573242, 9.5367431640625e-07, 9.5367431640625e-07, 1.1811695098876953, 1.4875000715255737, 1.6023555994033813, 2.195054054260254, 1.2703123092651367, 2.5626628398895264, 2.1296935081481934, 1.68040931224823, 1.9301981925964355, 1.5615262985229492, 0.7754058837890625, 1.3993552923202515, 1.6602312326431274, 1.9000598192214966, 1.3197660446166992, 2.174412727355957, 1.052206039428711, 0.4621647596359253, 1.4125641584396362, 1.2691144943237305, 1.9492015838623047, 1.4256060123443604, 2.475856065750122, 9.5367431640625e-07, 1.1547554731369019, 2.164454221725464, 9.5367431640625e-07, 0.390797883272171, 1.82555091381073, 0.9883832931518555, 0.562504768371582, 1.9908629655838013, 0.7862328886985779, 2.0101163387298584, 1.574929118156433, 2.9335296154022217, 1.7981027364730835, 1.9499496221542358, 1.0475611686706543, 1.6595399379730225, 1.453884243965149, 2.295079231262207, 1.102089762687683, 1.5847216844558716, 2.371670722961426, 2.4393014907836914, 1.6912871599197388, 1.2764256000518799, 9.5367431640625e-07, 1.877053141593933, 1.6402273178100586, 1.424208641052246, 1.3983700275421143, 0.8161039352416992, 2.400712013244629, 2.2884771823883057, 0.9698380827903748, 1.4818581342697144, 1.623055100440979, 9.5367431640625e-07, 1.8147438764572144, 1.635305404663086, 2.0196619033813477, 0.8571758270263672, 1.4564749002456665, 2.118535041809082, 2.171353340148926, 1.6759138107299805, 1.5821985006332397, 1.061020851135254, 2.264955997467041, 1.8395243883132935, 1.870869517326355, 1.5869405269622803, 1.8147233724594116, 1.6719063520431519, 1.6560791730880737, 1.559639811515808, 1.82548987865448, 2.6317381858825684, 2.2250325679779053, 1.417112112045288, 0.9377250671386719, 1.1998203992843628, 1.3376024961471558, 2.206587553024292, 1.5557880401611328, 1.4648977518081665, 1.6332817077636719, 0.9302731156349182, 1.896742343902588, 2.3849971294403076, 1.6789960861206055, 1.8543882369995117, 9.5367431640625e-07, 1.267547607421875, 9.5367431640625e-07, 0.0005720257759094238, 0.049234986305236816, 0.00664233323186636, 0.0, 0.0010385083733126521, 0.0, 0.0, 2.6047229084724677e-07, 0.01181948371231556, 6.500065501313657e-05, 0.0, 0.025409018620848656, 0.02248663455247879, 0.008313238620758057, 0.015447589568793774, 0.06303524225950241, 0.0, 0.0, 0.0015144699718803167, 0.05021403357386589, 0.033516526222229004, 0.059431493282318115, 0.04721803590655327, 0.0, 0.0, 0.03402411937713623, 0.0075893402099609375, 0.0, 0.000664955354295671, 0.00015159964095801115, 0.048262376338243484, 0.0, 0.0018739992519840598, 0.09182033687829971, 0.039060596376657486, 0.0038857460021972656, 0.022408200427889824, 0.012530681677162647, 0.009308937937021255, 0.017927665263414383, 0.031235169619321823, 1.1086463928222656e-05, 0.002418946009129286, 0.0, 0.004959711339324713, 0.041628122329711914, 0.001306295394897461, 0.0, 0.03846561908721924, 0.030222704634070396, 6.437301180994837e-08, 0.0, 0.005096138454973698, 0.0, 0.004422579891979694, 0.0, 0.031695544719696045, 0.062276799231767654, 0.04510832577943802, 0.0, 0.0501675121486187, 0.0, 0.05574244260787964, 0.0009069448569789529, 0.0053579858504235744, 0.0, 0.0387997031211853, 0.003314814530313015, 0.0807395800948143, 0.054399147629737854, 0.0, 0.041628122329711914, 0.03509746491909027, 0.0, 0.0, 0.004882514476776123, 0.0013629322638735175, 0.06746155023574829, 0.006005359813570976, 0.01889139600098133, 0.0, 0.0, 0.00930178165435791, 0.0, 0.04198469966650009, 0.01853412389755249, 0.013396177440881729, 0.04924900829792023, 0.046571072190999985, 0.0, 0.016043614596128464, 0.0, 0.0020152926445007324, 0.00833192653954029, 0.003265380859375, 0.0005842530517838895, 5.9604643443123e-10, 0.09041278809309006, 0.02312157303094864, 0.0, 0.006803017109632492, 0.042842473834753036, 0.006532114464789629, 0.027412766590714455, 0.006354517303407192, 0.018055379390716553, 0.016570184379816055, 0.0, 0.07653409987688065, 0.06093936413526535, 0.0, 0.055298127233982086, 0.0, 5.9604643443123e-10, 0.0, 0.00014172673400025815, 7.188319841588964e-07, 0.03846561908721924, 0.0, 0.05128916725516319, 0.04433514177799225, 0.03514524921774864, 0.003876757575199008, 1.4305114426349519e-08, 0.03559465706348419, 0.0029597878456115723, 0.0003117203596048057, 0.001174701377749443, 0.015041353181004524, 0.062101658433675766, 0.05305451899766922, 0.010164334438741207, 0.043437182903289795, 0.08640551567077637, 0.02574741840362549, 0.0009953975677490234, 0.0, 3.24499596899841e-05, 7.906138489488512e-05, 0.03853100538253784, 0.009371264837682247, 9.453296661376953e-05, 0.04568150267004967, 0.03948081284761429, 2.38418573772492e-09, 0.0, 0.05529302358627319, 0.03846561908721924, 0.0005500250845216215, 0.04630931839346886, 0.0, 0.0, 8.972883370006457e-05, 0.004056155681610107, 0.042238324880599976, 0.03846561908721924, 0.062101658433675766, 1.7285346984863281e-06, 0.0037306647282093763, 0.0, 0.03403213620185852, 0.03821954131126404, 0.007968827150762081, 0.00028872728580608964, 0.0, 0.0004595553909894079, 0.0, 2.0265579436795633e-08, 0.025750763714313507, 0.0, 0.002940952777862549, 0.00011579930287552997, 5.960464477539063e-08, 0.0017734789289534092, 0.08758766204118729, 1.3113021850585938e-06, 0.049289997667074203, 0.02188706398010254, 6.82765239616856e-05, 0.03547411412000656, 0.04890136048197746, 0.0010082870721817017, 0.09417987614870071, 0.022896120324730873, 0.057247359305620193, 0.045361220836639404, 0.028622448444366455, 0.0042545367032289505, 0.005239727906882763, 0.0011519789695739746, 0.008682149462401867, 0.004166607279330492, 0.044886231422424316, 7.80510890763253e-05, 0.0021342039108276367, 0.025984516367316246, 0.0, 0.026739809662103653, 0.0, 0.011457828804850578, 0.0008643698529340327, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.04502059891819954, 0.0009533452684991062, 0.04202387109398842, 0.015027965418994427, 0.00410237954929471, 1.3954639143776149e-05, 1.19209286886246e-09, 0.004250050522387028, 0.034012939780950546, 0.0027789699379354715, 0.0226406529545784, 0.023972392082214355, 0.0, 0.041628122329711914, 0.050519902259111404, 5.960464477539062e-07, 0.001926107332110405, 0.008155226707458496, 0.0708322525024414, 0.0004933535819873214, 0.009609833359718323, 0.01174461841583252, 0.0, 6.478666909970343e-05, 0.0, 0.030955379828810692, 0.0011048471787944436, 0.0002513617218937725, 0.007758900988847017, 0.006200278643518686, 0.04227335751056671, 0.07415975630283356, 0.0122609231621027, 0.010072720237076283, 0.012182116508483887, 0.017823902890086174, 0.03919167071580887, 0.0309562087059021, 0.0, 0.03789025545120239, 0.041628122329711914, 0.0, 1.823902130126953e-05, 0.0011938214302062988, 0.0005228912923485041, 0.004257035907357931, 0.010050652548670769, 0.038463953882455826, 0.015491707250475883, 0.045361220836639404, 0.0637897253036499, 0.0, 0.03454941138625145, 0.0498347282409668, 0.00825202465057373, 0.0, 0.0, 0.0, 0.05104376748204231, 0.051554735749959946, 0.032817985862493515, 0.05632689222693443, 0.00653288047760725, 0.0003492319374345243, 0.0, 0.0, 0.040220487862825394, 0.004605600144714117, 6.079673653403006e-07, 0.016681673005223274, 0.0, 0.010659174993634224, 0.004482310265302658, 0.026593247428536415, 0.002230703830718994, 0.0293202493339777, 0.0, 0.0052988165989518166, 0.03961218148469925, 0.05538519099354744, 0.07085771858692169, 0.0005188590148463845, 0.05529302358627319, 0.004755261354148388, 0.010815290734171867, 0.009690344333648682, 0.00045293569564819336, 0.0007979869842529297, 5.719661658076802e-06, 0.0, 0.03846561908721924, 0.022568173706531525, 0.062110960483551025, 0.12053205817937851, 0.3544481694698334, 0.09004760533571243, 0.09438516199588776, 0.3192572593688965, 0.32940977811813354, 6.464202240705815e-15, 1.2241060961637289e-14, 1.512081882230551e-14, 0.1717807799577713, 0.23580972850322723, 0.10148165374994278, 0.2161933034658432, 0.16413649916648865, 1.1344225865216225e-14, 0.20467343926429749, 0.11822348088026047, 0.22054797410964966, 0.23466546833515167, 0.1354188323020935, 0.22489841282367706, 0.09323403984308243, 0.11373721808195114, 0.3509841859340668, 0.10354459285736084, 5.299015248133327e-15, 0.2298799306154251, 0.07722597569227219, 0.28688696026802063, 0.12242648750543594, 1.1795203994026306e-14, 0.21231871843338013, 0.1921406090259552, 0.26097553968429565, 0.03842408210039139, 0.22631755471229553, 0.04901887848973274, 0.316408634185791, 0.04554933309555054, 0.08425658196210861, 0.1994837075471878, 0.09974879026412964, 0.07276112586259842, 0.22581760585308075, 0.17763268947601318, 0.0061621773056685925, 0.1387617439031601, 0.307326078414917, 0.0737062320113182, 0.22217310965061188, 0.09775817394256592, 0.08082050085067749, 0.23287467658519745, 0.2367592602968216, 0.2958735227584839, 0.027531156316399574, 0.2863447964191437, 0.25172173976898193, 0.12033511698246002, 0.3562775254249573, 0.028856316581368446, 0.09890587627887726, 0.2084917575120926, 0.196572944521904, 0.2353558987379074, 0.31180834770202637, 0.18802706897258759, 0.10271342843770981, 0.42561039328575134, 0.10050855576992035, 0.08665343374013901, 0.22613565623760223, 0.1138291135430336, 0.3994034230709076, 0.16656255722045898, 0.10599283128976822, 0.00385706196539104, 1.5114106933231466e-14, 0.12109849601984024, 0.17130881547927856, 0.17455771565437317, 0.10262452811002731, 0.18761172890663147, 9.642813653956087e-15, 0.22426395118236542, 0.19486075639724731, 0.30757808685302734, 0.0027450411580502987, 0.10420764982700348, 0.1582481563091278, 0.1155763790011406, 0.106765516102314, 0.10867587476968765, 1.4103791444734955e-14, 0.23443932831287384, 0.24225912988185883, 0.10516627877950668, 0.022296223789453506, 1.2838135333189792e-14, 0.30991002917289734, 0.10897651314735413, 0.18411152064800262, 0.2247430682182312, 0.09834548085927963, 0.08264699578285217, 0.35738879442214966, 0.23797911405563354, 0.3174505829811096, 0.10945092886686325, 0.11824043095111847, 0.1582164764404297, 0.11521852016448975, 0.13455358147621155, 0.4451387822628021, 0.0832592099905014, 0.35431256890296936, 0.20766322314739227, 0.015785768628120422, 5.781973952899942e-15, 0.23822417855262756, 0.1668737381696701, 0.08199365437030792, 0.2286403924226761, 0.044031884521245956, 0.11534810066223145, 0.08984102308750153, 0.1630222648382187, 0.08377879858016968, 0.3440883159637451, 0.11542388051748276, 0.07809021323919296, 0.10328231751918793, 0.0996680036187172, 0.09735928475856781, 0.11339332163333893, 0.09271637350320816, 0.17677970230579376, 0.2199310064315796, 9.174603486867064e-15, 0.10052201896905899, 0.09685526043176651, 0.330636203289032, 0.10319026559591293, 0.2815673053264618, 0.16900634765625, 0.1639566719532013, 0.018377985805273056, 0.09927348047494888, 0.0950952097773552, 0.21605809032917023, 0.2108621597290039, 0.060789041221141815, 0.11452484130859375, 0.07272720336914062, 0.10784587264060974, 0.24671994149684906, 0.0004825931682717055, 0.35966750979423523, 0.10169854015111923, 0.10550817847251892, 0.0355394147336483, 0.28050610423088074, 0.17981120944023132, 0.09177976101636887, 0.2163369357585907, 0.20247788727283478, 9.255575601459839e-15, 1.471158840636675e-14, 0.09375274181365967, 0.1064339429140091, 0.23487010598182678, 0.10353559255599976, 0.08152084052562714, 0.09562428295612335, 0.09303237497806549, 0.11517079919576645, 0.17381413280963898, 0.1977243721485138, 4.5741671783616766e-07, 0.01426172535866499, 0.09105342626571655, 0.11003901064395905, 0.005181223154067993, 0.038591817021369934, 0.10700341314077377, 0.31246477365493774, 0.1972900927066803, 0.3067454695701599, 0.2701184153556824, 0.12250448763370514, 0.0796145349740982, 0.10049367696046829, 0.010821078903973103, 0.09084449708461761, 0.16689682006835938, 0.3064942955970764, 0.22985008358955383, 9.152978735723662e-15, 0.1091814935207367, 0.2338864505290985, 0.08478306233882904, 0.006399495527148247, 0.06802982836961746, 0.18855075538158417, 4.426778835533475e-15, 0.1100069209933281, 0.1017642542719841, 0.18598505854606628, 0.0963490828871727, 0.25095146894454956, 0.32418346405029297, 0.2119263857603073, 0.18870118260383606, 0.10517165809869766, 0.16943110525608063, 0.20349881052970886, 0.00045294486335478723, 0.10793399810791016, 0.22728689014911652, 0.008396482095122337, 0.21868939697742462, 1.2426335019289064e-14, 0.10405776649713516, 0.42904868721961975, 9.447034693692465e-15, 0.11260166019201279, 0.35609352588653564, 0.0855269581079483, 0.1636687070131302, 1.0633549975876816e-14, 1.1655936530904649e-14, 0.2354561984539032, 0.22697997093200684, 3.876468729482408e-15, 0.04896445944905281, 0.11897376924753189, 0.3185681700706482, 0.1874265968799591, 1.0335832294477033e-14, 0.22388604283332825, 0.19037075340747833, 0.3390013575553894, 0.12172906845808029, 0.1713247001171112, 0.34414809942245483, 0.08607156574726105, 0.00014103316061664373, 0.11033507436513901, 0.08199311792850494, 0.19066230952739716, 0.16069816052913666, 0.10817556828260422, 0.09105226397514343, 0.11963330954313278, 0.1184777021408081, 0.16625437140464783, 0.13381236791610718, 0.07686720788478851, 0.0003375867672730237, 0.4444033205509186, 0.2274811565876007, 0.10568162798881531, 0.1105426549911499, 0.07957936823368073, 0.1962491124868393, 0.11744643747806549, 5.411284383094201e-15, 0.10618765652179718, 0.4689997136592865, 0.19019770622253418, 0.09677661955356598, 0.25206077098846436, 0.0895916149020195, 0.15637639164924622, 0.22634047269821167, 0.1925721913576126, 0.2751515209674835, 0.251078724861145, 0.08434261381626129, 0.005380831193178892, 0.07921809703111649, 0.11762800067663193, 0.07248979061841965, 0.21284763514995575, 0.0862092599272728, 0.10296737402677536, 0.02555139549076557, 7.254125685557389e-15, 1.1219238530552327e-14, 0.1402016282081604, 1.3696825147864206e-14, 1.4854254165672792e-14, 0.0938338041305542, 0.10332050174474716, 0.11343789100646973, 0.08745037019252777, 0.21402326226234436, 0.3191412389278412, 0.2173794060945511, 0.33423328399658203, 9.130280494689941, 22.50123405456543, 26.971464157104492, 10.786139488220215, 11.361392974853516, 21.396835327148438, 29.653818130493164, 26.356351852416992, 7.930558204650879, 17.111412048339844, 4.665748596191406, 14.799884796142578, 9.056830406188965, 22.16739273071289, 3.438617467880249, 28.16724967956543, 38.47552490234375, 33.912841796875, 18.391592025756836, 9.2758150100708, 43.409706115722656, 6.6271209716796875, 23.33917236328125, 4.244720458984375, 8.697479248046875, 6.249063968658447, 8.804367065429688, 11.669273376464844, 14.683554649353027, 16.96483612060547, 28.52582550048828, 6.354095458984375, 9.05252742767334, 20.605018615722656, 26.548187255859375, 6.978149890899658, 14.330397605895996, 16.131683349609375, 6.30509090423584, 18.70411491394043, 4.28289794921875, 4.529571533203125, 29.863773345947266, 21.13313865661621, 24.571449279785156, 8.2796630859375, 7.092926025390625, 5.517383098602295, 10.91156005859375, 8.464981079101562, 24.197221755981445, 6.901824951171875, 17.52956771850586, 9.416717529296875, 13.9542236328125, 13.186799049377441, 4.880516052246094, 15.327499389648438, 35.18901062011719, 8.127518653869629, 15.504714965820312, 1.4697418212890625, 10.617568969726562, 11.973136901855469, 8.224508285522461, 24.321334838867188, 7.132248401641846, 14.957533836364746, 9.282150268554688, 23.531661987304688, 40.069091796875, 4.7003631591796875, 7.0296783447265625, 20.680946350097656, 7.100287914276123, 29.314237594604492, 8.512603759765625, 4.4756011962890625, 12.488815307617188, 25.628202438354492, 17.52705192565918, 5.554046630859375, 10.73136043548584, 6.345832347869873, 12.886802673339844, 16.96733856201172, 6.128448486328125, 15.196044921875, 9.733384132385254, 10.28741455078125, 3.0001068115234375, 17.113754272460938, 25.81853485107422, 8.276833534240723, 10.706451416015625, 7.611105918884277, 25.48723602294922, 20.05014419555664, 7.77117919921875, 15.623122215270996, 2.7439591884613037, 4.995242595672607, 38.11097717285156, 11.190388679504395, 22.60560417175293, 6.31834077835083, 35.805870056152344, 22.631927490234375, 11.448715209960938, 6.05357027053833, 4.0823974609375, 5.0746002197265625, 8.713714599609375, 12.36119556427002, 6.757080078125, 6.028911590576172, 7.049641132354736, 4.521539211273193, 14.456596374511719, 8.60709285736084, 7.042510986328125, 25.26807975769043, 5.515138626098633, 11.221156120300293, 6.069084167480469, 17.089157104492188, 14.892191886901855, 25.939559936523438, 10.061904907226562, 24.79627799987793, 38.423789978027344, 14.57457160949707, 5.0556793212890625, 18.637039184570312, 28.020721435546875, 35.37745666503906, 8.4617919921875, 7.475982666015625, 36.00115966796875, 7.358365535736084, 31.060869216918945, 12.279960632324219, 12.551105499267578, 8.0672607421875, 19.401885986328125, 25.939544677734375, 3.5369176864624023, 5.4129486083984375, 18.566598892211914, 7.956218242645264, 14.093634605407715, 8.465801239013672, 12.157440185546875, 10.394624710083008, 12.276885986328125, 20.436737060546875, 14.028656005859375, 6.520524024963379, 18.250988006591797, 26.9373779296875, 5.663121223449707, 22.87276268005371, 12.381880760192871, 6.07537841796875, 15.301300048828125, 11.465972900390625, 22.768009185791016, 5.9294281005859375, 11.47696590423584, 6.050511837005615, 29.470365524291992, 17.74433135986328, 10.96759033203125, 6.096588134765625, 11.495924949645996, 22.626005172729492, 11.916183471679688, 16.34412384033203, 7.033294677734375, 29.44903564453125, 13.403434753417969, 5.254879474639893, 10.482139587402344, 8.142645835876465, 33.84446716308594, 5.3434295654296875, 2.2245330810546875, 17.75160026550293, 7.036837100982666, 11.604240417480469, 14.348960876464844, 4.679004192352295, 6.00537109375, 8.929397583007812, 16.613712310791016, 9.854127883911133, 14.91886043548584, 5.6263885498046875, 25.04534912109375, 6.692190170288086, 0.7853619456291199, 17.416061401367188, 15.231658935546875, 23.08431053161621, 2.869546413421631, 17.526763916015625, 9.960614204406738, 3.9515767097473145, 3.930168390274048, 3.447509765625, 11.596205711364746, 8.654685974121094, 7.35498046875, 8.271438598632812, 8.826937675476074, 6.996866703033447, 11.011276245117188, 15.144018173217773, 10.84368896484375, 17.484642028808594, 5.2930145263671875, 14.271491050720215, 26.10100746154785, 24.033597946166992, 12.171798706054688, 5.373318195343018, 9.77341365814209, 13.13983154296875, 24.799650192260742, 14.49277400970459, 26.80794334411621, 6.1918182373046875, 42.8431396484375, 17.978666305541992, 20.65717315673828, 6.692592620849609, 12.454559326171875, 10.859858512878418, 6.8062744140625, 12.079803466796875, 24.532461166381836, 7.5106658935546875, 2.0399322509765625, 7.387443542480469, 17.90656852722168, 5.924034118652344, 17.43426513671875, 7.00921630859375, 18.247543334960938, 8.001114845275879, 5.037689208984375, 18.44434356689453, 8.542109489440918, 10.720909118652344, 8.89255428314209, 13.016647338867188, 7.9723052978515625, 5.0276031494140625, 18.033952713012695, 15.805547714233398, 8.357467651367188, 35.11768341064453, 5.9172821044921875, 7.8290252685546875, 5.111572265625, 17.248321533203125, 7.5948944091796875, 6.0028839111328125, 6.002575397491455, 20.994918823242188, 7.08172607421875, 8.03533935546875, 8.802665710449219, 9.41196346282959, 27.519428253173828, 21.939847946166992, 10.6646728515625, 21.179906845092773, 5.27242374420166, 13.876771926879883, 5.425141334533691, 7.660369873046875, 7.717006683349609, 4.205935955047607, 9.465347290039062, 13.705485343933105, 13.765830993652344, 17.17876434326172, 14.651458740234375, 6.80322265625, 7.076812744140625, 4.339286804199219, 4.001739501953125, 12.131881713867188, 9.323394775390625, 8.458999633789062, 17.485904693603516, 12.400680541992188, 8.590052604675293, 11.966252326965332, 2.029552459716797, 1.682525873184204, 2.6501970291137695, 2.4994401931762695, 1.7220596075057983, 1.6646592617034912, 1.64002525806427, 1.6591978073120117, 1.356223702430725, 0.8555858135223389, 0.8747358322143555, 9.5367431640625e-07, 1.8721215724945068, 2.436966896057129, 1.6467397212982178, 0.668269157409668, 1.4028981924057007, 1.3252897262573242, 2.2590627670288086, 2.63155460357666, 2.1925430297851562, 2.058547258377075, 1.5722473859786987, 0.06805896759033203, 1.0929434299468994, 1.2810391187667847, 2.1172475814819336, 1.8256609439849854, 2.146066665649414, 1.717489242553711, 1.9562503099441528, 2.448383092880249, 1.2587876319885254, 1.1788681745529175, 1.2147207260131836, 0.9497918486595154, 1.2797058820724487, 1.241013765335083, 2.1931638717651367, 1.8480770587921143, 1.459084391593933, 9.5367431640625e-07, 9.5367431640625e-07, 1.859445571899414, 1.6114530563354492, 2.602247953414917, 2.242201805114746, 1.9970579147338867, 2.3337326049804688, 1.4673070907592773, 1.6363004446029663, 1.356368064880371, 9.5367431640625e-07, 0.5236978530883789, 9.5367431640625e-07, 2.861567258834839, 1.9858475923538208, 1.8983923196792603, 1.7613863945007324, 2.591771125793457, 1.2302465438842773, 2.587397336959839, 1.417144775390625, 1.3483346700668335, 1.746881365776062, 1.895332932472229, 1.1369915008544922, 1.0972646474838257, 1.5651406049728394, 0.9338188171386719, 1.0468558073043823, 1.7894700765609741, 1.9716360569000244, 2.1152596473693848, 1.0187309980392456, 1.3174450397491455, 1.4040344953536987, 1.5991395711898804, 0.6766137480735779, 0.24751585721969604, 1.691823124885559, 1.2759827375411987, 0.8834390044212341, 2.266324043273926, 1.1253067255020142, 1.469111442565918, 1.6998299360275269, 0.3689146041870117, 1.6148595809936523, 2.098818778991699, 1.5800836086273193, 1.9185646772384644, 9.5367431640625e-07, 1.1004308462142944, 0.6505865454673767, 1.2490471601486206, 2.455767869949341, 1.6729116439819336, 1.3783386945724487, 0.9192686080932617, 1.6834814548492432, 1.5940603017807007, 9.5367431640625e-07, 2.156968355178833, 1.6788491010665894, 2.5942022800445557, 1.606776237487793, 2.26054048538208, 9.5367431640625e-07, 1.8760719299316406, 1.357935905456543, 1.4343671798706055, 2.223313093185425, 1.7091021537780762, 1.1496819257736206, 2.625541925430298, 9.5367431640625e-07, 2.3633241653442383, 2.471513271331787, 2.0484094619750977, 2.006260871887207, 2.219578742980957, 2.354893445968628, 0.9718816876411438, 1.4768494367599487, 0.9383573532104492, 2.1500651836395264, 2.1732702255249023, 1.5394964218139648, 9.5367431640625e-07, 2.4116275310516357, 0.0496438592672348, 0.9945917129516602, 1.741658091545105, 1.6831109523773193, 1.1042717695236206, 1.7744017839431763, 2.0993242263793945, 1.9191182851791382, 0.6959867477416992, 1.7062691450119019, 1.7411013841629028, 1.7744415998458862, 0.4450279772281647, 2.1406984329223633, 2.177030086517334, 1.310341715812683, 1.3380426168441772, 1.4226199388504028, 2.7076199054718018, 1.8909310102462769, 1.576346755027771, 9.5367431640625e-07, 2.390650510787964, 9.5367431640625e-07, 1.9088901281356812, 0.575770378112793, 1.9723849296569824, 0.1865835189819336, 1.3331327438354492, 1.3675673007965088, 1.959958791732788, 1.4393433332443237, 1.9090576171875, 3.374375581741333, 2.459911823272705, 1.3224419355392456, 1.2252084016799927, 1.5277633666992188, 1.2099285125732422, 1.32001793384552, 1.897600769996643, 2.96787691116333, 0.21177959442138672, 1.67287015914917, 1.5343389511108398, 1.642983317375183, 2.239748239517212, 2.0522568225860596, 1.5476864576339722, 1.259442687034607, 1.1379698514938354, 1.5245351791381836, 1.3330903053283691, 0.9097728729248047, 1.7425533533096313, 1.5611448287963867, 2.104123830795288, 1.4665707349777222, 2.0223875045776367, 2.9021971225738525, 1.1017698049545288, 0.8843070864677429, 1.9883774518966675, 2.590223550796509, 1.6260616779327393, 2.4884772300720215, 1.6840838193893433, 1.9122610092163086, 1.5452545881271362, 1.75133216381073, 1.7544182538986206, 1.8895554542541504, 1.690810203552246, 1.1920722723007202, 1.7854586839675903, 9.5367431640625e-07, 9.5367431640625e-07, 1.6254644393920898, 1.6378639936447144, 1.6835929155349731, 1.8439468145370483, 0.23608218133449554, 1.4502313137054443, 2.33961820602417, 2.1537163257598877, 9.5367431640625e-07, 1.387365698814392, 1.7568100690841675, 1.621490240097046, 1.779030680656433, 2.905308723449707, 1.3552160263061523, 1.1165229082107544, 1.5002645254135132, 1.8586314916610718, 1.5694326162338257, 3.172246217727661, 1.8298702239990234, 0.902207612991333, 2.056567430496216, 1.76231849193573, 1.3136318922042847, 1.1763792037963867, 1.7218797206878662, 1.9294912815093994, 2.145075798034668, 2.301935911178589, 2.4693572521209717, 2.0943288803100586, 2.8075168132781982, 1.692624807357788, 2.85335373878479, 2.1038734912872314, 1.485482096672058, 0.6870489120483398, 9.5367431640625e-07, 9.5367431640625e-07, 1.446107029914856, 0.9931229948997498, 1.273018717765808, 1.9175416231155396, 2.1876981258392334, 0.672364354133606, 0.8937005400657654, 2.8524084091186523, 1.7016944885253906, 1.4027413129806519, 1.5292186737060547, 1.830423355102539, 1.8338247537612915, 1.8609932661056519, 1.0769062042236328, 3.3354527950286865, 1.9541490077972412, 1.6552170515060425, 2.028608798980713, 1.4179182052612305, 1.4282338619232178, 2.8038976192474365, 1.8441399335861206, 1.3676822185516357, 1.3810148239135742, 1.2337675094604492, 0.8550774455070496, 1.4732723236083984, 2.2839560508728027, 1.976011037826538, 2.6974828243255615, 0.847775399684906, 2.0173397064208984, 1.7643150091171265, 1.702189564704895, 2.620941638946533, 0.6612445116043091, 1.8003225326538086, 0.7300328016281128, 1.1649084091186523, 0.7677725553512573, 1.7898544073104858, 1.428908348083496, 2.1167726516723633, 2.2958831787109375, 1.956896185874939, 1.7513307332992554, 2.0126113891601562, 0.6908074617385864, 9.5367431640625e-07, 0.9143134355545044, 1.5828262567520142, 0.03891909122467041, 0.00040966272354125977, 0.05529302358627319, 0.002495288848876953, 0.006915080361068249, 0.030434846878051758, 0.041628122329711914, 0.035752177238464355, 0.045098330825567245, 0.0708322525024414, 0.029016513377428055, 0.0028502976056188345, 0.07608135789632797, 0.0, 0.01732097752392292, 0.00027740179211832583, 0.01249040849506855, 0.0025501030031591654, 0.03849232196807861, 0.013268806971609592, 0.06072559207677841, 0.009782016277313232, 0.0, 0.0001343375479336828, 0.0, 0.0046693990007042885, 0.039468202739953995, 0.006641366984695196, 0.01924055814743042, 0.04179835692048073, 0.0, 5.809068534290418e-05, 0.0021028495393693447, 0.03406384214758873, 0.0, 4.589557647705078e-06, 0.00010746895713964477, 0.021017184481024742, 0.006644904613494873, 0.0, 0.0006819468690082431, 0.027531685307621956, 0.0012585526565089822, 0.05529302358627319, 0.041628122329711914, 0.00043921469477936625, 0.0334334634244442, 0.02962294965982437, 3.2297968573402613e-05, 0.043620605021715164, 0.010860421694815159, 0.0, 0.034973353147506714, 0.07345367223024368, 0.004481554497033358, 0.02933761477470398, 0.0192835982888937, 0.008241071365773678, 0.009447005577385426, 0.0199664868414402, 0.021825144067406654, 0.0011698120506480336, 0.0, 0.0, 0.0498347282409668, 0.05272990092635155, 5.413770486484282e-05, 0.0017241459572687745, 0.0, 0.020197927951812744, 0.019296782091259956, 0.029103612527251244, 0.0642547681927681, 0.031573567539453506, 0.002516329288482666, 0.012320518493652344, 0.015653617680072784, 0.0033092540688812733, 0.08764999359846115, 0.011628031730651855, 0.00048059344408102334, 0.0, 0.018655838444828987, 0.03545111045241356, 0.008985301479697227, 0.08979833126068115, 3.7586687540169805e-06, 0.004216745495796204, 0.0020519602112472057, 5.006849823985249e-05, 0.008313893340528011, 0.05536847934126854, 0.0033209919929504395, 0.010249785147607327, 0.00796365737915039, 0.056998975574970245, 0.0498347282409668, 0.0008598482236266136, 0.0022431088145822287, 0.09115634858608246, 0.0, 0.0, 0.0008979469421319664, 0.000877081707585603, 0.0, 0.07418912649154663, 0.004145113285630941, 0.12296254932880402, 0.01092490367591381, 0.0, 0.10284155607223511, 0.05167430639266968, 0.03846561908721924, 0.03747216984629631, 0.035752177238464355, 0.03872963413596153, 0.0, 0.0498347282409668, 0.0, 0.002583156106993556, 0.007525804918259382, 1.6266106968032545e-06, 0.00011474012717371807, 0.0, 0.0650022029876709, 0.041628122329711914, 0.062101658433675766, 0.017018212005496025, 7.1525572131747595e-09, 0.08206957578659058, 0.0015228986740112305, 0.0, 0.006757285445928574, 0.028776854276657104, 0.0067594051361083984, 0.006474196910858154, 0.004659963771700859, 0.0, 0.03310321643948555, 0.013439549133181572, 0.00020742713240906596, 0.039834797382354736, 0.0, 0.012026150710880756, 0.04886479675769806, 0.03208751231431961, 0.0, 1.6539692296646535e-05, 0.001401867251843214, 0.0024456451646983624, 0.052216749638319016, 0.0, 0.005998613312840462, 3.1238794235832756e-06, 0.008529809303581715, 1.19209286886246e-09, 0.058487605303525925, 0.00033074317616410553, 0.06088709831237793, 0.020318781957030296, 0.004295945633202791, 0.0, 0.0, 0.03936019167304039, 6.210804031070438e-07, 0.0, 0.004311704076826572, 0.009600462391972542, 0.015889495611190796, 0.03489549458026886, 2.1994112842094182e-07, 0.0002355015167267993, 2.408027512501576e-06, 4.771769090439193e-05, 0.00031453371047973633, 0.0003247261047363281, 0.04014557600021362, 0.041628122329711914, 0.00011937796807615086, 0.04472091421484947, 0.037123024463653564, 0.008645514957606792, 0.036779358983039856, 1.19209286886246e-09, 0.01919209584593773, 6.395578384399414e-05, 0.0, 0.007056868635118008, 0.015277375467121601, 0.01255371980369091, 0.02227604389190674, 0.014973342418670654, 0.004993433132767677, 0.0071558356285095215, 0.11299184709787369, 0.04737234115600586, 0.03846561908721924, 0.024577200412750244, 0.017155705019831657, 0.04025609791278839, 0.009948906488716602, 0.05686373636126518, 0.045361220836639404, 5.9604643443123e-10, 0.009455467574298382, 0.023835130035877228, 0.0959620252251625, 0.05209526792168617, 0.03583734109997749, 0.061227597296237946, 0.007090907543897629, 0.009547916240990162, 0.020164599642157555, 0.0698869600892067, 0.0012901460286229849, 0.017308944836258888, 0.0, 0.0029973380733281374, 0.06752777099609375, 0.07951188087463379, 0.00039137183921411633, 0.005516354460269213, 3.3012031053658575e-05, 0.000629142508842051, 0.04161424562335014, 0.09859436750411987, 0.045361220836639404, 0.022083163261413574, 0.0, 0.0467374324798584, 0.07851433753967285, 0.08567851036787033, 0.05379343032836914, 0.0, 0.006098275538533926, 3.5762786065873797e-09, 0.014098156243562698, 0.009189781732857227, 0.005865752696990967, 0.05529302358627319, 0.02416786178946495, 0.0, 0.06540587544441223, 0.006951637100428343, 0.004525842610746622, 0.042804718017578125, 0.026223838329315186, 0.011799204163253307, 0.024710869416594505, 0.045361220836639404, 0.012305081821978092, 0.033448945730924606, 0.03846561908721924, 0.008390683680772781, 0.0, 0.0, 0.0009683972457423806, 0.01072673313319683, 0.0, 0.08888421952724457, 0.007053503300994635, 0.023888038471341133, 0.006817236542701721, 0.0005742311477661133, 0.0708322525024414, 0.0446154959499836, 0.05936199054121971, 0.0, 0.00028877437580376863, 0.0252089686691761, 0.03585415706038475, 0.0007441180641762912, 0.006637454032897949, 0.00982897263020277, 7.164478006416175e-07, 0.0753968134522438, 5.537271476896422e-07, 0.00019973218149971217, 0.05315990373492241, 0.0003954076673835516, 0.0418429970741272, 0.018816474825143814, 0.045361220836639404, 0.0, 0.03846561908721924, 0.007501186337321997, 0.04359883815050125, 0.050326891243457794, 6.0439109802246094e-05, 0.03846561908721924, 0.006262481212615967, 0.059608545154333115, 0.0029771924018859863, 0.006622381508350372, 0.011386752128601074, 0.006851440295577049, 0.0021985769271850586, 0.017154457047581673, 0.04789441078901291, 0.04486358165740967, 0.33209723234176636, 0.16524963080883026, 0.2864161729812622, 0.04099368304014206, 1.1709097407219815e-06, 0.14064417779445648, 0.3488849699497223, 0.09262044727802277, 0.11049488931894302, 0.2131241112947464, 0.3251364827156067, 0.11633177846670151, 0.23602131009101868, 0.0787162035703659, 0.08697023242712021, 0.086339570581913, 0.2006794661283493, 0.08753736317157745, 0.20763610303401947, 0.006366236601024866, 0.4291769564151764, 0.18145103752613068, 0.1035330668091774, 0.16171327233314514, 0.2344420701265335, 0.1949404925107956, 0.34170204401016235, 0.3279651701450348, 0.34994015097618103, 0.45285552740097046, 0.11392579972743988, 0.14088277518749237, 0.09485593438148499, 0.2315068244934082, 0.09885364025831223, 1.2683473893284735e-14, 1.3104130783681955e-14, 0.155432790517807, 0.32756537199020386, 0.4038507044315338, 0.30637961626052856, 0.1906098574399948, 0.0849345251917839, 0.4928564429283142, 0.02043442241847515, 0.2941136658191681, 1.772475144434793e-07, 0.07683314383029938, 0.35418617725372314, 1.473052975713325e-14, 0.15710526704788208, 0.08579333126544952, 0.03235672786831856, 0.3370378911495209, 0.34452468156814575, 0.0930989608168602, 0.19521552324295044, 0.0963873490691185, 0.16335353255271912, 0.18406717479228973, 0.24463531374931335, 0.45241355895996094, 0.1483236402273178, 0.07938708364963531, 0.11531726270914078, 0.17092998325824738, 0.20023483037948608, 0.20935168862342834, 0.21336917579174042, 0.11384782195091248, 0.13756760954856873, 0.10690832138061523, 1.4160916193730732e-14, 0.37784141302108765, 0.09012383967638016, 0.18913128972053528, 0.09298618882894516, 5.736755522527245e-15, 0.22489644587039948, 0.11642688512802124, 0.18007804453372955, 0.23807066679000854, 0.21271201968193054, 0.19945335388183594, 0.3330543041229248, 0.10704188793897629, 0.1935068815946579, 0.31683722138404846, 0.20601430535316467, 0.08726707845926285, 0.33294478058815, 0.08405280858278275, 0.03848971799015999, 0.43261247873306274, 6.92920045885885e-15, 0.007654828950762749, 0.18036511540412903, 1.3620887797109911e-14, 0.326366126537323, 0.18329162895679474, 0.11140395700931549, 0.08982711285352707, 1.2818897520891753e-14, 0.0173591747879982, 0.11698184907436371, 0.001359282643534243, 0.35087481141090393, 0.46595990657806396, 0.22786276042461395, 0.10701534897089005, 0.18975961208343506, 0.03696564584970474, 0.03716055676341057, 0.3279333710670471, 0.21605165302753448, 0.26236218214035034, 0.11897655576467514, 0.22350122034549713, 0.0892580971121788, 0.18856146931648254, 0.3263912796974182, 0.19810760021209717, 0.17376606166362762, 0.19584424793720245, 0.13741348683834076, 0.1550721377134323, 0.2855440378189087, 1.2887283572921276e-14, 0.1850743591785431, 0.4560367166996002, 0.44872885942459106, 0.1278744488954544, 0.23040889203548431, 0.4298210144042969, 0.1164705902338028, 0.23790767788887024, 0.06630149483680725, 0.09060641378164291, 0.22911617159843445, 0.1457003802061081, 0.2060527354478836, 0.2302640676498413, 0.41938817501068115, 0.025631168857216835, 0.18011562526226044, 0.34099870920181274, 4.328013523334203e-15, 0.1895226389169693, 0.2939872741699219, 0.10793465375900269, 0.0682220384478569, 0.007422788068652153, 0.3209511637687683, 0.18378765881061554, 0.26337549090385437, 0.2436847686767578, 0.11056094616651535, 0.2085626870393753, 0.3267487585544586, 0.22366724908351898, 0.23204748332500458, 0.3569892942905426, 0.2631063163280487, 0.11555995792150497, 0.19808661937713623, 0.08661161363124847, 0.23383843898773193, 0.0893612876534462, 0.3530905842781067, 0.29266810417175293, 0.1959347426891327, 0.04779558628797531, 0.23167575895786285, 0.0182566586881876, 0.3184596598148346, 0.19904112815856934, 0.0827883705496788, 0.022023681551218033, 0.001107846270315349, 0.24132056534290314, 0.1814505010843277, 0.4411548376083374, 0.19191983342170715, 0.09840095043182373, 0.43426284193992615, 0.23352372646331787, 8.843893025138778e-15, 0.2336224764585495, 0.2139388918876648, 0.09448964893817902, 0.2619260549545288, 0.22935226559638977, 0.0006942573236301541, 0.013613205403089523, 0.09860143810510635, 0.20586559176445007, 0.23298798501491547, 0.1175360307097435, 0.1862529069185257, 0.08625953644514084, 0.09401699155569077, 0.0986144170165062, 0.2988654673099518, 0.2136358916759491, 0.1595166027545929, 0.1164637953042984, 0.2015131711959839, 0.22622089087963104, 0.5757315158843994, 5.952175059255327e-15, 0.10659061372280121, 0.11164764314889908, 0.1534564197063446, 0.3225809335708618, 0.2050839215517044, 0.08170978724956512, 1.1530939031845384e-14, 0.10343917459249496, 0.3106960654258728, 7.0224782681093355e-15, 0.11541736125946045, 0.3730507493019104, 0.0006377898971550167, 0.0935838371515274, 0.20679862797260284, 7.580218970690191e-15, 0.36210379004478455, 0.09625882655382156, 0.17274104058742523, 0.02013462968170643, 0.19677844643592834, 0.11153259128332138, 0.09594341367483139, 0.12726005911827087, 0.3905116617679596, 0.11523418128490448, 0.23396284878253937, 0.344561904668808, 0.19014282524585724, 0.08155802637338638, 0.1750555783510208, 0.10496385395526886, 0.15449564158916473, 0.1558385193347931, 0.007464896887540817, 0.13542476296424866, 0.1717350333929062, 0.09039517492055893, 0.2230089157819748, 0.1016097217798233, 0.22849126160144806, 0.043273430317640305, 0.08403430879116058, 0.13635820150375366, 0.1341024786233902, 0.07894633710384369, 0.13113263249397278, 6.937827856745571e-05, 0.014966114424169064, 0.4405375123023987, 0.19396649301052094, 0.19887378811836243, 0.19366995990276337, 0.26191645860671997, 0.13880817592144012, 0.1559009552001953, 0.11704341322183609, 2.198109314122121e-06, 0.2479785680770874, 0.45747843384742737, 0.23881752789020538, 0.17924748361110687, 0.08666110038757324, 1.4817814808281912e-14, 0.060711439698934555, 0.22081539034843445, 0.19190481305122375, 0.1825951337814331, 0.34914472699165344, 0.23477241396903992, 0.1917072832584381, 0.08492093533277512, 0.18305636942386627, 0.12387170642614365, 0.001033526612445712, 0.23039992153644562, 0.29345911741256714, 0.11863815039396286, 0.22102148830890656, 0.23689119517803192, 0.3093835711479187, 0.007274021860212088, 0.23026502132415771, 0.3542449474334717, 0.22557540237903595, 0.23703911900520325, 0.07230480015277863, 7.662821735721081e-05, 0.3565739095211029, 0.4314669072628021, 45.47797775268555, 4.007270336151123, 9.981422424316406, 7.062463283538818, 22.3140869140625, 12.110724449157715, 9.608535766601562, 9.427254676818848, 22.469161987304688, 32.63772201538086, 30.45782470703125, 9.53089427947998, 15.472567558288574, 15.928337097167969, 32.79461669921875, 26.40260124206543, 5.348602294921875, 37.0308837890625, 31.126609802246094, 14.791519165039062, 3.5586700439453125, 17.29701042175293, 17.315902709960938, 9.550003051757812, 7.842218399047852, 27.93425750732422, 18.4749755859375, 5.6177659034729, 45.75914001464844, 18.93602752685547, 13.211410522460938, 7.21630859375, 16.19195556640625, 4.3548126220703125, 15.132598876953125, 13.31015396118164, 11.555190086364746, 15.5050048828125, 19.53670310974121, 24.558273315429688, 8.986587524414062, 8.453170776367188, 25.065887451171875, 18.832015991210938, 6.638744354248047, 12.906264305114746, 12.297636032104492, 24.340789794921875, 33.44607162475586, 24.10784149169922, 19.26789665222168, 7.250842094421387, 36.58591842651367, 7.989593505859375, 32.04887390136719, 25.406269073486328, 41.91427993774414, 8.28220272064209, 16.858970642089844, 8.097827911376953, 10.229820251464844, 23.480148315429688, 19.484272003173828, 13.588424682617188, 27.48699951171875, 7.41845703125, 7.7718353271484375, 6.217875957489014, 47.261878967285156, 6.125821590423584, 7.714821815490723, 13.232955932617188, 5.146751403808594, 18.403732299804688, 21.5494327545166, 10.247772216796875, 17.20064926147461, 20.51533317565918, 30.693979263305664, 19.832687377929688, 29.390600204467773, 35.90980529785156, 17.614126205444336, 6.570681571960449, 14.735214233398438, 14.948309898376465, 13.6492919921875, 9.512296676635742, 4.502220153808594, 34.80585479736328, 16.68975830078125, 22.405380249023438, 5.7071990966796875, 6.979538440704346, 24.33186149597168, 30.81809425354004, 23.962881088256836, 10.610865592956543, 13.184541702270508, 10.754852294921875, 7.991811275482178, 21.545578002929688, 64.86946868896484, 14.308327674865723, 8.454535484313965, 10.265809059143066, 16.13384246826172, 13.711318016052246, 67.63408660888672, 6.256500244140625, 33.96514892578125, 19.99609375, 2.9793853759765625, 36.302093505859375, 10.925673484802246, 14.388444900512695, 14.486724853515625, 9.196922302246094, 8.6856107711792, 7.8404388427734375, 10.624674797058105, 11.322404861450195, 8.231114387512207, 27.025541305541992, 6.980852127075195, 25.18316650390625, 8.340347290039062, 8.834610939025879, 15.382963180541992, 4.351043701171875, 12.159036636352539, 15.707608222961426, 16.00616455078125, 12.31732177734375, 18.92589569091797, 32.32660675048828, 22.764423370361328, 18.000587463378906, 16.307907104492188, 11.440546989440918, 7.276695251464844, 17.22638702392578, 13.322768211364746, 7.160001754760742, 38.40092086791992, 6.02886962890625, 16.661895751953125, 16.0142822265625, 7.7390899658203125, 17.39460563659668, 4.0009002685546875, 5.0146636962890625, 10.575139999389648, 14.931327819824219, 16.995513916015625, 13.965385437011719, 9.347610473632812, 22.092620849609375, 11.68729305267334, 8.445645332336426, 16.013242721557617, 23.10340690612793, 5.0348358154296875, 36.57048797607422, 4.1304473876953125, 19.32927703857422, 22.651702880859375, 12.624046325683594, 12.754103660583496, 17.96827507019043, 9.749504089355469, 6.0843048095703125, 21.63429069519043, 20.649343490600586, 11.194915771484375, 9.01712417602539, 15.955632209777832, 14.825469970703125, 8.732818603515625, 15.054611206054688, 8.730767250061035, 9.710419654846191, 17.943132400512695, 26.41182518005371, 10.211005210876465, 8.876282691955566, 13.919569969177246, 8.60577392578125, 43.37404251098633, 8.526430130004883, 7.26678466796875, 14.044281005859375, 10.964892387390137, 32.2171630859375, 9.004425048828125, 33.20111083984375, 8.57904052734375, 7.367938041687012, 12.226580619812012, 9.32073974609375, 17.545822143554688, 7.889380931854248, 9.671157836914062, 8.52667236328125, 22.82175636291504, 25.391098022460938, 7.932136058807373, 4.00091552734375, 6.076816082000732, 38.43186950683594, 12.391266822814941, 19.742591857910156, 8.004852294921875, 8.332260131835938, 16.33261489868164, 14.832037925720215, 6.992358684539795, 5.371124267578125, 9.251684188842773, 24.511051177978516, 45.170989990234375, 38.047889709472656, 12.187932014465332, 42.15394592285156, 21.190963745117188, 6.881608009338379, 7.430858135223389, 15.715956687927246, 11.467289924621582, 10.48499870300293, 13.6868896484375, 2.7735595703125, 6.981199264526367, 5.687075614929199, 10.26154613494873, 10.293180465698242, 19.32220458984375, 11.92464828491211, 5.7262420654296875, 5.819610595703125, 56.88954162597656, 13.16396427154541, 10.89569091796875, 24.0380859375, 14.848793983459473, 12.728583335876465, 17.081613540649414, 12.291740417480469, 8.818634986877441, 10.004989624023438, 17.61851692199707, 8.234541893005371, 8.711409568786621, 9.89764404296875, 17.935142517089844, 7.00925350189209, 10.299423217773438, 14.060770988464355, 6.338816165924072, 15.155261039733887, 19.37017822265625, 8.966851234436035, 9.981572151184082, 8.536187171936035, 7.680762767791748, 10.529571533203125, 6.9388580322265625, 22.32878875732422, 19.393661499023438, 6.412045955657959, 7.379636287689209, 3.0201644897460938, 11.172286987304688, 8.639739990234375, 12.147942543029785, 8.337646484375, 5.594256401062012, 10.998079299926758, 6.54571533203125, 10.595882415771484, 8.019222259521484, 15.132522583007812, 5.393516540527344, 24.851102828979492, 13.37606143951416, 49.3280029296875, 10.004792213439941, 9.086636543273926, 10.184844970703125, 11.250136375427246, 4.0652923583984375, 11.980414390563965, 5.815152645111084, 22.048507690429688, 60.58027267456055, 6.425445556640625, 12.703497886657715, 11.171339988708496, 79.60659790039062, 17.995407104492188, 1.3947935104370117, 2.30903959274292, 1.058160662651062, 9.5367431640625e-07, 1.8214635848999023, 1.09044349193573, 2.0272939205169678, 1.4615154266357422, 2.0382416248321533, 1.3698022365570068, 2.3062095642089844, 1.7904289960861206, 1.344018578529358, 1.6306812763214111, 2.782498359680176, 1.53258216381073, 1.3152048587799072, 1.2649586200714111, 1.9905859231948853, 1.4075798988342285, 0.29751110076904297, 1.1940116882324219, 2.680742025375366, 2.295557737350464, 1.0081982612609863, 1.8872911930084229, 1.1705961227416992, 1.140761375427246, 0.8332299590110779, 1.9804885387420654, 2.191161870956421, 2.254019021987915, 1.0374722480773926, 2.160764694213867, 0.82451331615448, 1.323560118675232, 9.5367431640625e-07, 1.6067724227905273, 1.9624601602554321, 1.72325599193573, 1.8642433881759644, 2.137091636657715, 1.90430748462677, 1.126246452331543, 1.446864128112793, 1.745754361152649, 9.5367431640625e-07, 2.904858112335205, 1.5392426252365112, 1.0467385053634644, 2.1441855430603027, 1.3742046356201172, 1.266000509262085, 2.030573606491089, 1.7588223218917847, 1.4399689435958862, 2.477343797683716, 1.837945818901062, 1.4951092004776, 3.383681058883667, 1.981330394744873, 1.8920410871505737, 1.3101595640182495, 1.6531990766525269, 2.0890278816223145, 1.3310186862945557, 2.1775870323181152, 1.6793978214263916, 1.186640739440918, 1.8529462814331055, 1.4611941576004028, 2.867161989212036, 9.5367431640625e-07, 1.224097728729248, 1.73473060131073, 2.8516342639923096, 9.5367431640625e-07, 2.254983425140381, 1.500374674797058, 2.4685921669006348, 1.6779890060424805, 0.20654010772705078, 1.620261549949646, 1.2117469310760498, 1.2198855876922607, 2.6634650230407715, 1.3808883428573608, 2.2728302478790283, 1.3652164936065674, 1.3508027791976929, 1.6376111507415771, 1.0131340026855469, 0.6630048751831055, 1.581315279006958, 1.6724368333816528, 1.1160953044891357, 1.5289009809494019, 1.087319254875183, 1.5164581537246704, 2.144778251647949, 2.150871753692627, 1.3096455335617065, 1.6637014150619507, 1.7715544700622559, 0.7478628158569336, 2.1586592197418213, 2.501850128173828, 2.3300294876098633, 1.1242170333862305, 1.8535088300704956, 1.5541448593139648, 1.347176432609558, 2.745856761932373, 1.190327525138855, 2.6914801597595215, 2.714325428009033, 1.6878204345703125, 1.4895256757736206, 1.1685476303100586, 1.4940001964569092, 1.3634346723556519, 1.5538228750228882, 1.6509671211242676, 2.306161642074585, 9.5367431640625e-07, 1.6839874982833862, 1.3426694869995117, 1.5641220808029175, 1.5305242538452148, 3.0388927459716797, 1.829548716545105, 1.274287223815918, 1.3521877527236938, 9.5367431640625e-07, 2.1576192378997803, 1.2467228174209595, 1.5082441568374634, 1.3329572677612305, 1.6544121503829956, 1.3425759077072144, 2.0969655513763428, 1.1750918626785278, 1.7693781852722168, 2.132626533508301, 1.901408314704895, 1.1509275436401367, 1.11528480052948, 2.422548532485962, 1.5013474225997925, 2.1656885147094727, 1.403414249420166, 2.2907533645629883, 1.52031672000885, 0.25226306915283203, 0.5295324325561523, 1.0764150619506836, 1.7068833112716675, 1.9650928974151611, 2.3128862380981445, 2.5828568935394287, 2.54579496383667, 9.5367431640625e-07, 1.38523268699646, 1.6854543685913086, 2.321223020553589, 1.9921660423278809, 1.9494271278381348, 2.4447684288024902, 1.0628690719604492, 1.9863964319229126, 0.9281492233276367, 1.601888656616211, 1.8806874752044678, 2.1659231185913086, 0.29750919342041016, 2.150822639465332, 1.7421234846115112, 2.1583001613616943, 2.361579418182373, 1.957541823387146, 0.9259376525878906, 1.6197975873947144, 3.352023124694824, 1.6717041730880737, 2.6752467155456543, 1.113398551940918, 1.6371688842773438, 1.845467448234558, 9.5367431640625e-07, 2.230499267578125, 1.568928599357605, 0.31879329681396484, 2.336174964904785, 1.5561836957931519, 1.5267657041549683, 1.6536132097244263, 1.5906609296798706, 1.9794950485229492, 2.674860715866089, 1.6913557052612305, 1.4344323873519897, 2.266313076019287, 0.5436506271362305, 0.8420019149780273, 1.3496613502502441, 0.9579458236694336, 0.9141419529914856, 1.086038589477539, 2.2839269638061523, 1.9976046085357666, 1.0486358404159546, 2.376826524734497, 1.4238386154174805, 1.084106683731079, 2.0800328254699707, 2.223374605178833, 1.2855767011642456, 1.1353615522384644, 2.554438829421997, 1.5738838911056519, 1.503218650817871, 1.441908836364746, 2.6862521171569824, 1.357600212097168, 2.155405282974243, 1.6013131141662598, 1.4167743921279907, 1.5834804773330688, 1.1260756254196167, 1.1634896993637085, 3.8806936740875244, 1.2867251634597778, 1.9065542221069336, 1.2152966260910034, 1.5995595455169678, 1.7102898359298706, 0.3677492141723633, 1.6397864818572998, 1.5045576095581055, 2.969496965408325, 0.8891915678977966, 0.17261290550231934, 1.9261826276779175, 0.048397522419691086, 1.2863316535949707, 2.3394768238067627, 1.6274709701538086, 1.1679085493087769, 2.0208518505096436, 1.8799457550048828, 1.2592496871948242, 1.9614410400390625, 1.6628522872924805, 2.5647201538085938, 1.3302028179168701, 1.8530714511871338, 2.3076391220092773, 1.4232186079025269, 2.162949562072754, 1.4072256088256836, 0.8075628280639648, 1.433233618736267, 1.488795280456543, 1.7315030097961426, 1.5232326984405518, 1.6840734481811523, 1.2860687971115112, 1.551533818244934, 0.8880729675292969, 1.6943691968917847, 1.4945068359375, 1.6352965831756592, 1.8302773237228394, 0.37224864959716797, 1.30018949508667, 2.0576791763305664, 0.9290785193443298, 3.3111445903778076, 2.2377805709838867, 1.758750319480896, 1.620570182800293, 1.5477129220962524, 1.623923420906067, 1.4121074676513672, 1.3084630966186523, 1.196833610534668, 0.6647863388061523, 0.8771305084228516, 9.5367431640625e-07, 1.3173531293869019, 1.4015264511108398, 1.3185148239135742, 1.0946900844573975, 1.499225378036499, 1.8706319332122803, 1.3600378036499023, 2.397066831588745, 1.7633336782455444, 1.8140839338302612, 9.5367431640625e-07, 0.002437413902953267, 0.0048652892000973225, 0.0694977343082428, 0.00026770710246637464, 0.00900192465633154, 0.08835285902023315, 0.03423304110765457, 0.03504067659378052, 0.02642618864774704, 0.04544224590063095, 0.00028843877953477204, 0.060057997703552246, 0.0036366002168506384, 0.006050119176506996, 0.038333795964717865, 0.04162826016545296, 0.002346963156014681, 0.016550203785300255, 0.0, 0.031895339488983154, 0.00085772096645087, 0.0, 0.006908534560352564, 0.04660434648394585, 0.03754482418298721, 0.10240321606397629, 0.00043088197708129883, 0.016640126705169678, 0.09861244261264801, 3.2067298889160156e-05, 0.041628122329711914, 0.0009283887920901179, 0.0032851635478436947, 0.07710886746644974, 0.0, 0.0003855240356642753, 0.012023921124637127, 0.0, 0.02628031186759472, 0.02650306560099125, 0.007357906084507704, 0.009691007435321808, 0.004525140859186649, 0.009199092164635658, 0.032877206802368164, 0.0066195097751915455, 0.044623155146837234, 0.0498347282409668, 0.0066792964935302734, 0.07963363081216812, 0.017969395965337753, 0.04498846083879471, 0.0003535461437422782, 0.03861594200134277, 0.061894673854112625, 0.025731021538376808, 0.02557356469333172, 1.5889405403868295e-05, 0.0, 0.05865049362182617, 0.022874893620610237, 0.044504135847091675, 0.036316290497779846, 0.022413644939661026, 0.0498347282409668, 0.03939266502857208, 0.008714587427675724, 0.009935619309544563, 0.00033968687057495117, 8.620619155408349e-06, 0.010621816851198673, 0.023904617875814438, 0.027341138571500778, 0.03364068269729614, 0.0, 0.004274920094758272, 0.03881368413567543, 0.011301224119961262, 0.02444281615316868, 0.08533679693937302, 5.728006362915039e-05, 0.0, 0.001369727193377912, 0.014320570975542068, 0.04777603596448898, 0.014564150013029575, 0.030229860916733742, 0.0, 0.0, 0.032413072884082794, 0.02651922218501568, 0.0002224492927780375, 0.04199334979057312, 0.0498347282409668, 0.049890823662281036, 0.007950186729431152, 0.06445270776748657, 0.01803288236260414, 0.018444359302520752, 0.018672510981559753, 0.026894602924585342, 0.05096966028213501, 0.01238510012626648, 0.07093294709920883, 1.2576580047607422e-05, 0.02642502449452877, 0.0033852283377200365, 0.04060087725520134, 0.011766508221626282, 0.010824139229953289, 0.03808183968067169, 0.03579314798116684, 0.012321630492806435, 0.00032070695306174457, 0.05613997206091881, 0.028610171750187874, 0.0, 0.041628122329711914, 0.06291485577821732, 0.0067521617747843266, 0.0031533925794065, 0.02584073878824711, 0.035752177238464355, 0.12886787950992584, 0.022788288071751595, 0.10933941602706909, 0.027002710849046707, 0.07286113500595093, 0.07736478000879288, 0.0007663369178771973, 0.01015239953994751, 0.0008528006146661937, 0.010019659996032715, 0.07656610012054443, 0.07980024814605713, 0.009007462300360203, 0.013296196237206459, 0.01061172690242529, 0.0031606650445610285, 0.028104357421398163, 0.05285073071718216, 0.06890091300010681, 0.06797390431165695, 0.033494915813207626, 0.03479057550430298, 0.05818361043930054, 0.004341017920523882, 0.09859436750411987, 0.0037108068354427814, 0.003628435544669628, 0.020017871633172035, 0.03497941419482231, 0.007412954233586788, 0.00442387443035841, 1.5513896869379096e-05, 0.06797390431165695, 0.0, 0.052853941917419434, 0.004858115222305059, 0.0011968332109972835, 0.0031731128692626953, 0.08910459280014038, 0.042777642607688904, 0.018465697765350342, 0.06862729787826538, 0.0, 0.05206521973013878, 0.03316839039325714, 0.03339850902557373, 0.05966900289058685, 0.002906054724007845, 0.041628122329711914, 0.04150233045220375, 0.015387741848826408, 0.01617945171892643, 0.056070201098918915, 0.009806809015572071, 0.011672687716782093, 1.7881393032936899e-09, 0.0001437664031982422, 0.007246792316436768, 0.03980772942304611, 0.025607705116271973, 0.06685128808021545, 0.0005694037536159158, 0.01312745176255703, 0.07307076454162598, 0.04556769132614136, 0.015808964148163795, 0.0, 0.02050257846713066, 0.017376605421304703, 0.019414961338043213, 0.005531073082238436, 0.04540659859776497, 0.0010346657363697886, 0.0, 0.018137039616703987, 0.024426639080047607, 1.2338161070601927e-07, 0.023613156750798225, 0.023328270763158798, 0.014507906511425972, 0.09565800428390503, 0.08565270900726318, 0.053778648376464844, 0.01509144064038992, 0.13123196363449097, 0.08009254932403564, 0.015778064727783203, 0.03550928831100464, 0.04894811660051346, 0.08865618705749512, 0.0003353881766088307, 0.019768530502915382, 0.0, 0.043988898396492004, 0.00031191110610961914, 0.0, 0.017543433234095573, 0.05605478212237358, 0.12224024534225464, 0.05863367021083832, 0.01356460526585579, 0.041628122329711914, 0.0032840101048350334, 0.02333332784473896, 0.05143304541707039, 0.017160773277282715, 0.034243252128362656, 0.038835350424051285, 0.11775737255811691, 0.006613255478441715, 0.08158963918685913, 0.04544490575790405, 0.041628122329711914, 0.02839028835296631, 0.028479520231485367, 0.004467623773962259, 0.034652963280677795, 0.010141612030565739, 0.06595437228679657, 0.041811659932136536, 0.03908812254667282, 0.012486997991800308, 0.0005941462586633861, 0.005252243019640446, 0.0, 0.05398351699113846, 0.033370375633239746, 0.06140720844268799, 0.0003465324698481709, 0.011443412862718105, 0.045383382588624954, 0.008706629276275635, 0.011632487177848816, 0.01069861650466919, 0.007027762476354837, 0.0697905421257019, 0.010140023194253445, 0.04757179319858551, 0.048450883477926254, 0.0612071268260479, 0.09859436750411987, 0.0, 0.008725292049348354, 1.1990666280325968e-05, 0.0, 0.0010856848675757647, 0.008805212564766407, 0.062101658433675766, 0.0498347282409668, 0.019374709576368332, 0.03846561908721924, 0.03451840952038765, 0.0128716342151165, 0.02275087870657444, 0.014247932471334934, 0.00421857088804245, 0.02939058281481266, 0.03937045484781265, 0.06628674268722534, 0.05080186203122139, 0.05977235734462738, 0.0030231480486691, 0.007267771754413843, 0.0009376048692502081, 0.02136361040174961, 0.04194844514131546, 0.03699541091918945, 0.016677694395184517, 0.036426447331905365, 0.06076420098543167, 0.05283252149820328, 0.026805222034454346, 0.03339850902557373, 0.011420028284192085, 0.0, 0.04581686854362488, 0.014425039291381836, 0.39478200674057007, 0.2593453526496887, 0.22134366631507874, 0.22185465693473816, 0.299060195684433, 0.43068891763687134, 0.12287504225969315, 0.21056918799877167, 0.21101680397987366, 0.1698116511106491, 6.91236440848275e-15, 0.08784965425729752, 0.08164513111114502, 0.14014455676078796, 0.10527602583169937, 0.16425016522407532, 0.19421760737895966, 0.37811797857284546, 0.09321223944425583, 0.15831388533115387, 0.2090594470500946, 0.22304847836494446, 0.2484559267759323, 0.20462481677532196, 0.4670962393283844, 0.20896784961223602, 0.21759846806526184, 0.08176456391811371, 0.23301182687282562, 0.13968682289123535, 0.09441287070512772, 0.3352329432964325, 0.11794879287481308, 0.08970983326435089, 0.18914096057415009, 0.2158966064453125, 0.12124501913785934, 0.30101028084754944, 1.0776962818242336e-14, 0.11939803510904312, 1.1258474790735041e-14, 0.057501036673784256, 0.3274903893470764, 0.10358476638793945, 0.15595071017742157, 0.13797380030155182, 0.2931874692440033, 0.31148561835289, 0.002269506687298417, 0.21345384418964386, 0.00034231567406095564, 0.07599079608917236, 0.3165704011917114, 0.304176926612854, 0.1268475353717804, 0.08918610960245132, 0.24740035831928253, 0.30961325764656067, 0.44015562534332275, 0.2895132899284363, 0.16522258520126343, 0.25759437680244446, 0.19640854001045227, 0.45840299129486084, 0.2207915186882019, 0.10483632981777191, 0.17536552250385284, 0.1908990889787674, 8.508886821800843e-05, 0.1948879361152649, 0.11243585497140884, 0.21611613035202026, 0.05628758296370506, 0.37566015124320984, 0.044512394815683365, 0.18874883651733398, 0.1834050714969635, 0.08740933239459991, 0.22791464626789093, 0.30694136023521423, 0.14505553245544434, 0.21495741605758667, 0.017476698383688927, 0.1774996966123581, 0.31851616501808167, 0.012635339051485062, 0.22651511430740356, 0.3325746953487396, 0.3459487855434418, 0.1341884434223175, 0.1175803542137146, 0.2885156273841858, 0.09640060365200043, 0.10564550012350082, 0.20702454447746277, 0.1351228505373001, 0.3906319737434387, 0.3191567659378052, 0.21104910969734192, 0.3659485876560211, 0.26861584186553955, 0.19536086916923523, 0.0011062397388741374, 0.2711310386657715, 0.03250011056661606, 0.08757857233285904, 0.34455931186676025, 0.07704733312129974, 0.0767529159784317, 0.21053948998451233, 0.25184187293052673, 0.18350711464881897, 0.21436534821987152, 0.2265390306711197, 0.20825594663619995, 0.029971893876791, 0.035767827183008194, 0.23797504603862762, 0.43861258029937744, 0.051542848348617554, 0.22571270167827606, 0.0842951163649559, 0.3564257025718689, 0.09926698356866837, 0.10838405042886734, 0.26029813289642334, 0.19156686961650848, 0.127558633685112, 0.16873864829540253, 0.31879013776779175, 0.15104858577251434, 0.5551958680152893, 0.13559122383594513, 0.1922624111175537, 0.09687526524066925, 0.11521333456039429, 5.713398165490234e-15, 0.37355199456214905, 0.11315387487411499, 0.25742581486701965, 0.11495423316955566, 0.35653746128082275, 0.21832534670829773, 0.4377654790878296, 0.2618561387062073, 0.13505110144615173, 0.10465942323207855, 0.09469834715127945, 0.20964065194129944, 0.17420455813407898, 0.1158454567193985, 0.0023607329931110144, 1.1588828651592532e-14, 0.32051676511764526, 0.09581037610769272, 0.017520252615213394, 0.1420671045780182, 0.34839874505996704, 0.4279816746711731, 0.37582990527153015, 0.15394346415996552, 0.1071370393037796, 0.21553383767604828, 0.1719251424074173, 0.21011319756507874, 0.21587863564491272, 0.1903459131717682, 0.17959392070770264, 0.11239971220493317, 0.21337278187274933, 0.07800666987895966, 0.11884038895368576, 0.3273366093635559, 0.11555251479148865, 0.11169778555631638, 0.31907469034194946, 0.4893016815185547, 0.3803764879703522, 0.2249499261379242, 0.0984671413898468, 0.0028256296645849943, 0.10652655363082886, 0.22017812728881836, 0.12005019932985306, 5.7934347321927666e-15, 0.2462494969367981, 0.413720041513443, 0.19188934564590454, 0.22639137506484985, 5.672728725560766e-15, 0.09119607508182526, 0.2268257886171341, 0.311847984790802, 0.3404420018196106, 0.07675187289714813, 0.33240312337875366, 0.1852092295885086, 0.25477781891822815, 0.3321608006954193, 0.1935194581747055, 0.28772997856140137, 0.15607422590255737, 0.1156872883439064, 0.10572870075702667, 0.12609852850437164, 0.2235737144947052, 0.08597509562969208, 0.20848269760608673, 0.08212314546108246, 0.13271015882492065, 0.31881335377693176, 1.0104922642726038e-14, 0.32175448536872864, 0.14013010263442993, 0.5179452896118164, 0.08186753839254379, 0.26717984676361084, 0.08927445858716965, 0.18308094143867493, 0.39829879999160767, 0.11783227324485779, 0.19341163337230682, 0.1774400919675827, 0.24009020626544952, 0.3150056004524231, 0.40337106585502625, 0.32505789399147034, 0.08792480081319809, 0.337502121925354, 0.20236042141914368, 0.38388124108314514, 0.2839156687259674, 0.4373694658279419, 0.4801696538925171, 0.15842148661613464, 0.2183438092470169, 0.30463355779647827, 0.355661541223526, 0.11492690443992615, 0.3419865071773529, 0.2613257169723511, 0.06320241093635559, 0.277767151594162, 0.32722997665405273, 0.11914130300283432, 0.1096254512667656, 0.07190550118684769, 0.08880897611379623, 0.22203584015369415, 0.5592164993286133, 0.23097151517868042, 0.5596252083778381, 0.20609326660633087, 0.10940815508365631, 1.2130906020912761e-14, 0.08153877407312393, 0.09295818954706192, 0.09418436139822006, 0.2987520396709442, 1.584660367370816e-06, 0.19362442195415497, 8.022197374435696e-15, 0.603608250617981, 0.03558574244379997, 0.19173583388328552, 0.42215171456336975, 0.19312064349651337, 0.24799969792366028, 0.2658018469810486, 0.0808291807770729, 0.11150126904249191, 0.14984025061130524, 0.08504275977611542, 0.1597769558429718, 0.16975784301757812, 0.3112628757953644, 0.33321890234947205, 0.1422595977783203, 0.22086085379123688, 0.23775635659694672, 0.32992908358573914, 4.664543524926599e-15, 0.2343427985906601, 1.3437996443138762e-14, 0.3694887161254883, 0.0219999048858881, 0.08708228915929794, 0.1898920089006424, 5.293324457277199e-15, 0.08908136188983917, 0.2226024568080902, 0.07852824032306671, 0.23221206665039062, 0.1633051335811615, 0.334001749753952, 0.10331416130065918, 0.3364890217781067, 0.45128676295280457, 0.20804746448993683, 0.1890604943037033, 14.908133506774902, 30.770370483398438, 18.84271240234375, 16.12506103515625, 10.009275436401367, 8.597479820251465, 15.257975578308105, 12.037177085876465, 15.968231201171875, 21.05207633972168, 13.683761596679688, 8.243621826171875, 18.88142204284668, 46.98472595214844, 7.238887786865234, 14.388214111328125, 28.095279693603516, 16.391510009765625, 36.88035202026367, 10.712355613708496, 42.26899337768555, 52.35755157470703, 23.241703033447266, 10.701952934265137, 10.811659812927246, 37.43363952636719, 58.94451904296875, 18.868425369262695, 11.279098510742188, 28.344528198242188, 20.003982543945312, 18.58688735961914, 21.90679931640625, 23.8781681060791, 12.977736473083496, 43.87754821777344, 60.24531936645508, 30.387304306030273, 8.457476615905762, 16.18329620361328, 20.766273498535156, 20.693405151367188, 15.404433250427246, 9.397125244140625, 39.86237335205078, 26.54296875, 12.992213249206543, 6.3524394035339355, 6.0735321044921875, 22.454879760742188, 7.736537933349609, 29.589853286743164, 8.148040771484375, 18.5465087890625, 13.661849975585938, 29.123319625854492, 8.790611267089844, 3.8530185222625732, 17.853866577148438, 22.0723876953125, 46.34046936035156, 11.89922046661377, 12.713611602783203, 22.960693359375, 11.188199996948242, 14.082463264465332, 28.920194625854492, 10.226669311523438, 28.56195068359375, 18.00218391418457, 32.458370208740234, 10.763418197631836, 17.83591079711914, 30.0821533203125, 26.8983154296875, 19.50958251953125, 5.1331024169921875, 12.428326606750488, 8.558026313781738, 11.252731323242188, 24.5345458984375, 27.2391357421875, 10.036538124084473, 23.690353393554688, 24.242767333984375, 28.692245483398438, 7.72180700302124, 4.3126983642578125, 10.238395690917969, 51.98928451538086, 11.399580001831055, 12.62302017211914, 8.085956573486328, 32.39094543457031, 6.6967973709106445, 12.490388870239258, 12.063725471496582, 8.63482666015625, 8.883384704589844, 18.70629119873047, 20.351537704467773, 24.667030334472656, 12.362441062927246, 13.532294273376465, 8.253302574157715, 11.231796264648438, 17.68787956237793, 10.025436401367188, 11.534149169921875, 11.197096824645996, 9.731515884399414, 13.432089805603027, 18.55574607849121, 25.215911865234375, 11.885910034179688, 8.630852699279785, 13.13934326171875, 14.370842933654785, 21.97157096862793, 6.643842697143555, 16.61667251586914, 7.213104248046875, 11.621429443359375, 12.29278564453125, 9.958878517150879, 26.26043701171875, 6.995395183563232, 16.184593200683594, 26.85456657409668, 6.473241329193115, 11.880905151367188, 55.1759033203125, 6.791435241699219, 25.048131942749023, 20.36488151550293, 22.27430534362793, 4.0219573974609375, 17.39277458190918, 18.667022705078125, 7.067649841308594, 6.938568115234375, 15.263434410095215, 19.14141082763672, 9.689398765563965, 6.931830883026123, 12.6171875, 22.821218490600586, 14.780951499938965, 4.751466274261475, 22.944766998291016, 8.005424499511719, 8.25632381439209, 7.845062255859375, 11.360087394714355, 13.52719783782959, 9.149612426757812, 7.6478729248046875, 5.2168426513671875, 27.702787399291992, 47.4176025390625, 42.79638671875, 15.68087100982666, 35.33298110961914, 9.607369422912598, 12.043166160583496, 7.152864933013916, 25.6754150390625, 23.872650146484375, 25.066335678100586, 17.46064567565918, 6.061524391174316, 12.59039306640625, 11.526198387145996, 18.128158569335938, 24.917709350585938, 44.50990295410156, 22.5394287109375, 21.97187042236328, 7.028350830078125, 2.992889404296875, 11.126513481140137, 17.77452278137207, 17.32269287109375, 8.330322265625, 15.383925437927246, 26.889423370361328, 23.304035186767578, 4.678622245788574, 16.46819496154785, 20.414283752441406, 17.129196166992188, 9.94720458984375, 20.16050148010254, 33.540122985839844, 30.121469497680664, 29.563705444335938, 10.302970886230469, 35.613040924072266, 37.47709274291992, 24.85957145690918, 17.800827026367188, 27.77125358581543, 10.026872634887695, 24.79474639892578, 23.21735954284668, 27.744232177734375, 47.516693115234375, 11.198512077331543, 17.29389762878418, 10.148515701293945, 5.439483642578125, 7.936801433563232, 25.63398551940918, 23.61158561706543, 15.680877685546875, 14.635491371154785, 15.088027000427246, 16.09907341003418, 13.137457847595215, 44.49922561645508, 24.815242767333984, 15.048126220703125, 18.546875, 7.380998134613037, 13.646739959716797, 18.18897247314453, 8.994818687438965, 9.637642860412598, 23.829965591430664, 5.2457685470581055, 7.227378845214844, 14.266075134277344, 8.291947364807129, 15.464214324951172, 19.77829360961914, 12.735358238220215, 29.824508666992188, 26.711576461791992, 11.000213623046875, 41.461326599121094, 61.75474548339844, 8.656883239746094, 5.9944963455200195, 14.888656616210938, 5.99202823638916, 17.54759407043457, 7.994621276855469, 30.750289916992188, 15.326438903808594, 11.741679191589355, 29.236845016479492, 9.116747856140137, 13.239473342895508, 13.148517608642578, 13.639373779296875, 40.04136276245117, 26.386381149291992, 10.169830322265625, 31.35047721862793, 27.52855110168457, 23.574481964111328, 15.159149169921875, 21.974374771118164, 10.299407958984375, 15.959625244140625, 28.230775833129883, 4.026986598968506, 8.7492094039917, 27.453861236572266, 39.16632843017578, 8.088668823242188, 6.0396728515625, 21.97944450378418, 22.041671752929688, 11.49908447265625, 28.6636962890625, 13.783073425292969, 41.95574951171875, 9.926183700561523, 13.21774959564209, 20.17341423034668, 22.534637451171875, 12.022875785827637, 8.868270874023438, 55.21229553222656, 5.867034912109375, 12.346946716308594, 9.43045425415039, 6.580639362335205, 6.980727195739746, 23.530502319335938, 15.750323295593262, 6.027740478515625, 15.251803398132324, 34.0030403137207, 19.105358123779297, 11.67360782623291, 35.6119270324707, 8.979951858520508, 9.429535865783691, 1.7630159854888916, 1.7095022201538086, 1.9006112813949585, 2.0946474075317383, 1.4964874982833862, 1.1559443473815918, 2.0931150913238525, 1.91670560836792, 2.6264491081237793, 0.0733785629272461, 0.9650887846946716, 1.1375371217727661, 1.447916865348816, 1.2994316816329956, 1.4900014400482178, 0.3125419616699219, 1.1963529586791992, 1.7732822895050049, 2.2399327754974365, 1.436287760734558, 2.192690849304199, 1.5725812911987305, 2.16776180267334, 1.1822562217712402, 1.6851130723953247, 0.8115301132202148, 2.192570924758911, 1.28905189037323, 1.3671311140060425, 3.040828227996826, 1.2140717506408691, 1.916377067565918, 1.01842200756073, 1.4850366115570068, 2.403533458709717, 1.7143067121505737, 1.9007576704025269, 1.048653483390808, 3.1645660400390625, 2.2401089668273926, 1.1904670000076294, 1.9077595472335815, 2.647394895553589, 0.9889824390411377, 1.1001005172729492, 1.8809523582458496, 1.5403022766113281, 2.264049530029297, 1.8096033334732056, 1.3575714826583862, 1.7347948551177979, 1.1530842781066895, 1.8532439470291138, 1.4973899126052856, 1.5094823837280273, 2.5316853523254395, 1.1693929433822632, 1.6686480045318604, 1.729174017906189, 1.693581461906433, 2.6325786113739014, 1.1472185850143433, 1.4975697994232178, 2.0860893726348877, 1.472573161125183, 0.8385839462280273, 2.30755352973938, 1.7344170808792114, 1.2837553024291992, 1.9782708883285522, 1.6493862867355347, 1.0573692321777344, 2.2352235317230225, 1.7243887186050415, 2.2802882194519043, 1.6549978256225586, 1.4483975172042847, 2.4851274490356445, 1.1964941024780273, 0.8954285979270935, 1.1081284284591675, 1.539467692375183, 2.1722967624664307, 2.0707626342773438, 1.2721630334854126, 0.7827885150909424, 0.00015354156494140625, 1.1705613136291504, 1.4612994194030762, 1.2369985580444336, 1.2598732709884644, 1.1021106243133545, 2.5776207447052, 1.5618947744369507, 2.341052532196045, 2.352362871170044, 2.8404250144958496, 1.1499576568603516, 1.357232928276062, 1.2030935287475586, 1.6323097944259644, 1.5581016540527344, 0.8050088286399841, 2.5207269191741943, 1.9609535932540894, 1.8130300045013428, 1.963644027709961, 1.3798558712005615, 2.5349512100219727, 1.5030088424682617, 1.611383318901062, 1.3765525817871094, 2.5342764854431152, 1.2982865571975708, 2.120553731918335, 2.3900232315063477, 2.08939266204834, 1.6540250778198242, 2.1449835300445557, 0.7644580006599426, 9.5367431640625e-07, 2.1147382259368896, 1.1127796173095703, 2.576416015625, 2.4372432231903076, 1.7689924240112305, 1.2973356246948242, 1.7260323762893677, 1.052043080329895, 1.672477126121521, 2.1274590492248535, 2.133922576904297, 1.4515389204025269, 3.054640531539917, 1.683732271194458, 1.8572273254394531, 1.5099064111709595, 2.3273959159851074, 1.4792351722717285, 1.5000466108322144, 2.3363537788391113, 1.1092232465744019, 2.3775057792663574, 0.8504407405853271, 1.8248461484909058, 2.126392364501953, 1.738176941871643, 2.655898332595825, 2.0602006912231445, 1.4182809591293335, 2.795536994934082, 1.6708364486694336, 1.6187795400619507, 3.3112199306488037, 1.052226185798645, 1.2147893905639648, 1.650152564048767, 2.0754315853118896, 2.271740198135376, 2.2252511978149414, 2.1730542182922363, 1.554667592048645, 1.0206345319747925, 1.3875188827514648, 0.6445074081420898, 1.2740933895111084, 1.380924940109253, 2.0077531337738037, 1.5918645858764648, 1.3454102277755737, 1.5261883735656738, 1.207478404045105, 9.5367431640625e-07, 1.501360297203064, 2.289278745651245, 2.7264184951782227, 2.403599262237549, 1.6776647567749023, 1.611385464668274, 2.2017760276794434, 1.3929014205932617, 1.775343894958496, 2.246311664581299, 1.7707700729370117, 2.6594841480255127, 1.9949151277542114, 1.3766353130340576, 1.86683189868927, 1.6905393600463867, 1.795960545539856, 1.9947936534881592, 2.366246223449707, 1.2732093334197998, 9.5367431640625e-07, 2.4588375091552734, 2.0098540782928467, 2.313927173614502, 1.482075572013855, 1.593440055847168, 2.1409919261932373, 2.654332160949707, 1.5288381576538086, 0.200858011841774, 1.0774725675582886, 0.9904391169548035, 2.5994861125946045, 1.4168673753738403, 1.332839012145996, 1.624833345413208, 1.3559390306472778, 2.343292236328125, 1.5749263763427734, 2.914026975631714, 0.7969216704368591, 2.4905238151550293, 2.121495008468628, 1.6100847721099854, 0.6724081039428711, 1.06670081615448, 1.2305707931518555, 2.102044105529785, 1.3206369876861572, 2.4996020793914795, 0.8102959990501404, 1.1535520553588867, 1.6043826341629028, 2.4532291889190674, 2.8651444911956787, 2.1879634857177734, 1.141225814819336, 2.257666826248169, 1.2591009140014648, 2.768573760986328, 0.90458083152771, 1.6583967208862305, 2.4492692947387695, 1.9930251836776733, 1.990313172340393, 2.7585790157318115, 1.559573769569397, 1.4348394870758057, 1.6567254066467285, 1.3636902570724487, 1.638521432876587, 2.5927977561950684, 1.4915411472320557, 0.8976740837097168, 2.515416145324707, 2.3006410598754883, 9.5367431640625e-07, 1.7426170110702515, 2.1204373836517334, 2.0955612659454346, 0.6388084888458252, 9.5367431640625e-07, 1.9472506046295166, 2.742137908935547, 0.3009977340698242, 1.8230886459350586, 2.519373893737793, 2.25582218170166, 2.2883718013763428, 1.4207792282104492, 1.228920817375183, 1.8167084455490112, 1.9404821395874023, 1.7519705295562744, 2.6128642559051514, 1.73794424533844, 1.5350725650787354, 2.368622303009033, 1.594660758972168, 2.084223747253418, 1.9189095497131348, 1.4340362548828125, 1.2795429229736328, 1.237467646598816, 2.391742706298828, 1.3786882162094116, 0.0, 1.925759196281433, 3.571836471557617, 2.135756254196167, 1.2238035202026367, 1.222912311553955, 2.4186007976531982, 1.6233080625534058, 1.6303136348724365, 1.6932744979858398, 1.325523018836975, 1.8003188371658325, 1.4769028425216675, 2.1365983486175537, 2.1287431716918945, 2.5340662002563477, 1.3261213302612305, 1.2250717878341675, 2.1761693954467773, 2.5262370109558105, 1.4960508346557617, 0.011832067742943764, 0.11106261610984802, 0.006813460029661655, 0.06498663872480392, 0.049837809056043625, 0.05529302358627319, 0.082432322204113, 0.0456843376159668, 0.041994400322437286, 0.02010732889175415, 0.002720925724133849, 0.004203500226140022, 0.041221894323825836, 0.04208076372742653, 0.026004735380411148, 0.03812742233276367, 0.007999306544661522, 0.052071575075387955, 0.05483269691467285, 0.047101326286792755, 0.0, 0.02129477448761463, 0.03704126179218292, 0.03575229272246361, 0.0335642509162426, 0.10093609243631363, 0.08657326549291611, 0.014850497245788574, 0.0, 0.0048074740916490555, 5.960464122267695e-09, 0.02192891575396061, 0.02603243477642536, 0.0014956104569137096, 0.0, 0.0005212014657445252, 5.9604643443123e-10, 0.010199368000030518, 0.0013644653372466564, 0.05164482817053795, 0.03533655405044556, 0.0020619570277631283, 0.00010037422180175781, 0.026459412649273872, 0.12065993994474411, 0.04577558860182762, 0.0002732276916503906, 0.06280164420604706, 0.03811724856495857, 0.040695734322071075, 5.9604643443123e-10, 0.035752177238464355, 0.0229700468480587, 0.003948022145777941, 0.0, 0.02748728170990944, 0.030168646946549416, 0.03092920035123825, 2.8465985451475717e-05, 0.042042531073093414, 0.0, 0.004046594258397818, 0.05228899046778679, 0.06216450408101082, 0.014204263687133789, 0.005234703421592712, 0.0498347282409668, 0.013869292102754116, 0.045835208147764206, 0.013430514372885227, 0.04284781217575073, 0.0, 0.0, 0.0004736602131742984, 5.996226946081151e-07, 0.07949619740247726, 0.005287826061248779, 0.001324489712715149, 0.002070350106805563, 0.05621928721666336, 0.03706079721450806, 0.045008301734924316, 0.022682130336761475, 0.045541323721408844, 5.841255187988281e-06, 1.1920928955078125e-07, 0.04152905195951462, 0.04468514397740364, 0.016275355592370033, 0.00012403845903463662, 0.02757490612566471, 0.013715941458940506, 0.09071225672960281, 0.0, 0.07535266876220703, 0.030871007591485977, 0.013229472562670708, 0.06890299916267395, 0.0071727740578353405, 0.05992818623781204, 0.07595956325531006, 0.020814742892980576, 0.00026000916841439903, 0.104008249938488, 0.0012752085458487272, 0.0029671096708625555, 0.005282009020447731, 0.03235533833503723, 0.002146859187632799, 0.0, 0.07286113500595093, 0.018345190212130547, 0.07036810368299484, 0.0, 0.037243425846099854, 0.03339851275086403, 0.03446423262357712, 0.05325055494904518, 0.0, 0.033855509012937546, 7.2437524067936465e-06, 0.05639714002609253, 0.03389658033847809, 0.05786586552858353, 0.040807414799928665, 0.06684976071119308, 0.06797390431165695, 0.0, 0.10081040859222412, 0.002512173028662801, 0.005054384935647249, 0.001787365647032857, 0.05690456181764603, 0.06940467655658722, 0.03442684933543205, 0.04008002206683159, 0.03387194871902466, 0.009062954224646091, 0.025445226579904556, 0.040997378528118134, 0.028918618336319923, 0.025926891714334488, 0.07136315852403641, 0.0498347282409668, 0.0004125237464904785, 0.029959451407194138, 0.06346327811479568, 0.00012053071986883879, 0.0476909801363945, 0.028994835913181305, 0.08256804943084717, 0.045361220836639404, 0.0824844241142273, 0.006899645552039146, 0.04301648959517479, 0.05132174491882324, 0.029516279697418213, 0.045361220836639404, 0.059092044830322266, 0.00401082681491971, 0.0320054292678833, 0.03735709190368652, 0.12224024534225464, 0.041508980095386505, 0.04176247492432594, 0.061001650989055634, 0.0391523540019989, 0.04360648989677429, 0.01054797600954771, 0.0758216381072998, 0.02369532734155655, 0.041912734508514404, 0.06165846809744835, 0.01084977388381958, 0.004024684429168701, 0.01113194227218628, 0.07365356385707855, 0.011828508228063583, 0.0005176073173061013, 0.012222190387547016, 0.02253865823149681, 0.005092325620353222, 0.06545589864253998, 0.10409629344940186, 0.08414866030216217, 0.06227242946624756, 5.9604643443123e-10, 0.04178101569414139, 0.014719843864440918, 0.007280593737959862, 0.04297823831439018, 0.08659207820892334, 0.009279369376599789, 0.007300790399312973, 0.09313978254795074, 0.03846561908721924, 0.035752177238464355, 0.0061487555503845215, 0.0, 0.012293953448534012, 0.0027395719662308693, 0.058279894292354584, 0.05367545410990715, 0.015710890293121338, 0.062101658433675766, 0.014780993573367596, 0.04367009177803993, 0.0043315887451171875, 0.0023780076298862696, 0.023218274116516113, 0.07729808241128922, 0.07009028643369675, 0.08268710970878601, 0.05083908513188362, 0.008096507750451565, 0.009768260642886162, 0.0464823916554451, 0.035752177238464355, 0.0640617087483406, 0.0032740235328674316, 0.062176283448934555, 0.04848608747124672, 0.006896830629557371, 0.0016629134770482779, 0.03751664236187935, 0.03897999972105026, 0.0, 0.048014964908361435, 0.04783197119832039, 0.10189109295606613, 0.035095810890197754, 0.08361124992370605, 0.0, 0.05480855703353882, 0.03339850902557373, 0.00025242805713787675, 0.01227460615336895, 0.045387208461761475, 0.04893284663558006, 0.054202914237976074, 0.033323440700769424, 0.06652824580669403, 0.013917983509600163, 0.024294670671224594, 0.06217163801193237, 0.0005168324569240212, 0.03014403209090233, 0.0368536114692688, 0.0, 0.04682276025414467, 0.09785742312669754, 0.010503353551030159, 0.041217558085918427, 0.03339851275086403, 0.011022803373634815, 0.028947552666068077, 0.036025285720825195, 0.04174100235104561, 0.06607062369585037, 0.007002426311373711, 0.0, 0.041334331035614014, 0.07286113500595093, 0.04299077019095421, 0.024535933509469032, 0.07327381521463394, 0.00040604828973300755, 0.06729744374752045, 0.0498347282409668, 0.01587534137070179, 0.001335807959549129, 0.03339873254299164, 0.005425276234745979, 0.04497573897242546, 0.03509229049086571, 0.0010761832818388939, 0.01811133697628975, 0.0, 0.048664215952157974, 0.007230037357658148, 0.00947993528097868, 0.0009142797789536417, 0.030417263507843018, 0.03342517837882042, 0.06155566871166229, 0.07075235992670059, 0.022807352244853973, 0.07845325022935867, 0.026880625635385513, 0.009837508201599121, 0.024004096165299416, 0.005836710333824158, 0.016644062474370003, 0.009902309626340866, 0.08558964729309082, 0.017726778984069824, 0.010033538565039635, 0.0, 0.00011473894119262695, 0.023040689527988434, 0.16090324521064758, 0.12473388761281967, 0.34898844361305237, 0.2527608871459961, 0.2017725706100464, 0.2628028392791748, 0.32238686084747314, 0.37594208121299744, 0.34148940443992615, 0.18201740086078644, 0.34522250294685364, 0.18021488189697266, 0.09993314743041992, 0.2237149029970169, 0.31679290533065796, 0.4132187068462372, 0.11447504907846451, 0.4019525945186615, 0.15065352618694305, 0.33326148986816406, 0.10800930112600327, 0.44051632285118103, 0.3888908326625824, 0.23797276616096497, 0.022160839289426804, 0.2186434119939804, 0.20135553181171417, 0.22862175107002258, 0.1182059645652771, 0.29173576831817627, 4.28113406135194e-15, 0.2697078585624695, 0.2556016743183136, 0.4325466752052307, 0.23746901750564575, 0.3551684021949768, 0.44612371921539307, 0.16113220155239105, 0.044392090290784836, 0.3550918996334076, 0.28684017062187195, 0.07970217615365982, 0.4289058446884155, 0.2301870435476303, 0.30108407139778137, 0.22893820703029633, 0.28341802954673767, 0.23541642725467682, 0.01770874857902527, 0.4191927909851074, 0.10885243862867355, 0.07768268138170242, 0.2830325663089752, 0.19961567223072052, 0.24932453036308289, 0.4045606553554535, 0.17992191016674042, 0.2201247215270996, 0.13796097040176392, 0.3465157151222229, 0.1049576848745346, 0.3852006494998932, 0.27270224690437317, 0.09025567770004272, 0.3605565130710602, 0.19149406254291534, 0.4504217505455017, 0.302065908908844, 0.09557268768548965, 0.2290353775024414, 0.12050248682498932, 0.20432692766189575, 0.21421535313129425, 0.22243081033229828, 0.05861673876643181, 0.16220012307167053, 0.34435516595840454, 0.41793447732925415, 0.104181207716465, 0.28935664892196655, 0.07816558331251144, 0.2305966466665268, 0.19580577313899994, 0.32763180136680603, 0.25099629163742065, 0.6014494299888611, 0.2920978367328644, 0.14040805399417877, 0.25193119049072266, 0.21926890313625336, 0.43112319707870483, 0.10337451845407486, 0.12761801481246948, 0.31087079644203186, 0.33340153098106384, 0.5577490329742432, 0.12581628561019897, 8.84649934551748e-15, 0.08020683377981186, 0.37090879678726196, 0.22310860455036163, 0.10808850824832916, 0.08683166652917862, 0.10440786182880402, 0.3025274872779846, 0.38914909958839417, 0.5670896768569946, 0.2089897096157074, 0.4426199197769165, 0.5235960483551025, 0.3730093538761139, 0.29400110244750977, 0.5623235702514648, 0.06484854221343994, 0.07288123667240143, 0.09006009995937347, 0.19770771265029907, 0.3006543219089508, 0.13663604855537415, 0.2624634802341461, 0.19082927703857422, 0.17016446590423584, 0.29949793219566345, 0.11049514263868332, 0.31404390931129456, 0.3488505482673645, 0.14285308122634888, 0.21790988743305206, 0.27957549691200256, 0.5891890525817871, 0.23565475642681122, 0.167855367064476, 0.45376989245414734, 0.14455190300941467, 0.10059154033660889, 0.3631681799888611, 0.27594298124313354, 0.13762769103050232, 0.4096236228942871, 0.25056469440460205, 0.5398388504981995, 0.26657170057296753, 0.16975152492523193, 0.31668928265571594, 0.11008478701114655, 0.14915776252746582, 0.4765939712524414, 0.10747583210468292, 0.21184366941452026, 0.1342557668685913, 0.21477515995502472, 0.21273916959762573, 0.35703903436660767, 0.2245641052722931, 0.29136717319488525, 0.3019781708717346, 0.5925882458686829, 0.08143282681703568, 0.43586716055870056, 0.25079500675201416, 0.09728735685348511, 0.2161111831665039, 0.20939235389232635, 6.267819844651967e-05, 0.3165202736854553, 0.19726058840751648, 0.4555213153362274, 0.3360629081726074, 0.1808679848909378, 0.26888328790664673, 0.27131861448287964, 0.12119872868061066, 0.3311503529548645, 5.207160454234229e-15, 0.48360687494277954, 0.16858823597431183, 0.1728474348783493, 0.09429612755775452, 0.3554052710533142, 0.35404887795448303, 0.5504603385925293, 0.38875651359558105, 0.35406896471977234, 0.09956878423690796, 0.15967807173728943, 0.22024668753147125, 0.08438865840435028, 0.6008345484733582, 0.3271176218986511, 0.4511195421218872, 0.20869310200214386, 0.26742252707481384, 0.10026033222675323, 0.4133145809173584, 0.3028483986854553, 0.58265221118927, 0.3552554249763489, 0.14603103697299957, 0.2675943374633789, 0.5780006051063538, 0.08105053007602692, 1.0097883798934355e-14, 0.19630476832389832, 0.16962821781635284, 0.33203619718551636, 0.3461298942565918, 0.21323390305042267, 1.838096324036087e-07, 0.2305913269519806, 0.324568510055542, 0.11446932703256607, 0.08989421278238297, 1.276880483942408e-14, 0.19496937096118927, 0.19289875030517578, 0.23605775833129883, 0.16331367194652557, 0.27727293968200684, 0.2624388337135315, 0.26439768075942993, 0.3573268949985504, 0.2216213494539261, 0.10424232482910156, 0.3283769488334656, 0.10352445393800735, 0.47137823700904846, 0.12204396724700928, 0.27862977981567383, 0.21189244091510773, 0.2966049909591675, 0.3592914640903473, 0.3063409626483917, 0.33971789479255676, 0.3799775540828705, 0.34294024109840393, 0.20089499652385712, 0.20720306038856506, 1.1582590253936004e-14, 0.43624502420425415, 4.382879658976126e-15, 0.3128817677497864, 0.12885235249996185, 0.20976927876472473, 0.11846835911273956, 0.11744317412376404, 0.46213456988334656, 0.004743816331028938, 0.16525420546531677, 0.16168451309204102, 0.12587125599384308, 0.32487159967422485, 0.12604005634784698, 0.2891930639743805, 0.26689308881759644, 0.15670530498027802, 0.0003709377197083086, 0.2005186378955841, 0.33682507276535034, 0.08609096705913544, 0.6057778596878052, 0.3650626242160797, 0.6247915029525757, 0.1839824765920639, 0.025006284937262535, 0.03934597969055176, 0.28997930884361267, 0.1011611819267273, 0.2804429829120636, 0.29208803176879883, 0.16774895787239075, 0.14143355190753937, 0.11019796133041382, 0.10131434351205826, 0.2947484254837036, 0.08880224823951721, 0.2655544877052307, 0.09638766199350357, 0.31296074390411377, 0.2740621566772461, 0.2277144342660904, 0.05031200125813484, 0.09372261166572571, 0.30140915513038635, 0.18329191207885742, 0.3793308138847351, 0.19558314979076385, 0.18421275913715363, 0.11875583231449127, 0.17878204584121704, 0.00018734933109954, 0.19321538507938385, 0.2795623540878296, 0.5212626457214355, 0.30348411202430725, 0.21239186823368073, 0.1942983716726303, 0.20868055522441864, 0.11487821489572525, 0.19977787137031555, 0.09336747974157333, 60.34402084350586, 13.346510887145996, 11.803955078125, 22.82830047607422, 14.591815948486328, 11.724135398864746, 20.119041442871094, 48.068904876708984, 21.309473037719727, 18.82188606262207, 19.906036376953125, 22.011688232421875, 17.582069396972656, 18.52626609802246, 19.755929946899414, 9.79669189453125, 8.340658187866211, 23.229398727416992, 12.15277099609375, 59.41714096069336, 9.056243896484375, 22.247220993041992, 8.926559448242188, 20.128036499023438, 24.98805046081543, 8.099205017089844, 15.523818969726562, 7.4649200439453125, 15.650619506835938, 19.612960815429688, 37.22890853881836, 26.865018844604492, 8.985198974609375, 8.03897762298584, 12.155059814453125, 13.520599365234375, 11.150802612304688, 34.20780944824219, 15.987030029296875, 7.137183666229248, 17.748943328857422, 16.731674194335938, 26.861610412597656, 9.146740913391113, 6.1599884033203125, 16.30140495300293, 7.993018627166748, 8.68893814086914, 11.656813621520996, 14.4798583984375, 17.326862335205078, 7.507066249847412, 24.063949584960938, 28.484222412109375, 9.152872085571289, 21.738866806030273, 43.434139251708984, 27.40948486328125, 24.326034545898438, 12.4265718460083, 30.963790893554688, 12.603805541992188, 19.93507194519043, 23.498580932617188, 21.513229370117188, 16.958656311035156, 13.820335388183594, 8.408920288085938, 7.0652923583984375, 24.524442672729492, 38.46714782714844, 34.573123931884766, 13.973212242126465, 27.152313232421875, 26.455795288085938, 43.6844482421875, 14.446528434753418, 14.01568603515625, 20.557044982910156, 13.203383445739746, 36.97645568847656, 16.780868530273438, 14.710702896118164, 23.35400390625, 7.62188720703125, 31.11427116394043, 9.187445640563965, 16.200653076171875, 14.295018196105957, 38.62300109863281, 7.173104286193848, 20.30579948425293, 8.836400985717773, 18.511199951171875, 12.571816444396973, 12.978349685668945, 20.84077262878418, 9.067231178283691, 12.981977462768555, 27.59151840209961, 13.101512908935547, 7.753113746643066, 17.841766357421875, 11.258228302001953, 16.345252990722656, 46.48247528076172, 38.41604232788086, 24.914794921875, 12.714202880859375, 27.893407821655273, 13.393680572509766, 16.441343307495117, 14.020187377929688, 10.509384155273438, 9.893020629882812, 46.785125732421875, 12.675712585449219, 24.865966796875, 11.046313285827637, 13.819137573242188, 65.07467651367188, 17.85780906677246, 9.411078453063965, 12.100897789001465, 8.579147338867188, 29.180009841918945, 9.217453002929688, 69.44921875, 44.37043762207031, 27.31646728515625, 17.599916458129883, 30.924686431884766, 6.606184959411621, 10.272696495056152, 40.85773468017578, 25.791305541992188, 25.412826538085938, 15.626510620117188, 20.097625732421875, 15.316054344177246, 8.04241943359375, 31.7540283203125, 9.170524597167969, 19.576271057128906, 6.7831878662109375, 40.667938232421875, 12.479494094848633, 10.844220161437988, 6.2635345458984375, 21.533851623535156, 6.70745849609375, 16.443960189819336, 7.875244140625, 28.20820426940918, 16.826562881469727, 28.63938331604004, 20.83560562133789, 24.636215209960938, 21.44961929321289, 12.863496780395508, 26.7879638671875, 8.730424880981445, 13.8699951171875, 9.195820808410645, 26.961496353149414, 12.0250244140625, 29.103904724121094, 22.96578025817871, 18.474098205566406, 7.7796630859375, 10.04401683807373, 25.795194625854492, 11.246200561523438, 13.36589527130127, 14.92974853515625, 46.98537826538086, 11.249064445495605, 8.22946834564209, 6.9365234375, 12.421356201171875, 12.44054126739502, 12.446212768554688, 18.254676818847656, 14.624245643615723, 37.34818649291992, 21.374130249023438, 37.88143539428711, 8.36328125, 4.838944435119629, 52.8763427734375, 32.38835144042969, 19.4351806640625, 9.693140983581543, 17.91041374206543, 12.985893249511719, 51.84914779663086, 9.290101051330566, 7.361315727233887, 12.984916687011719, 9.110702514648438, 32.5771484375, 10.472329139709473, 20.1805419921875, 29.59516716003418, 17.330718994140625, 30.873769760131836, 4.7841477394104, 11.469467163085938, 20.663875579833984, 13.614450454711914, 10.22896671295166, 40.08720779418945, 19.775558471679688, 6.0038909912109375, 13.33107852935791, 16.797422409057617, 35.3592529296875, 24.344039916992188, 27.138938903808594, 9.367904663085938, 21.514291763305664, 5.762938499450684, 24.1676025390625, 11.670028686523438, 26.91655731201172, 32.58612060546875, 21.02876091003418, 8.276824951171875, 8.02459716796875, 50.786346435546875, 6.709930419921875, 40.13421630859375, 7.451929092407227, 9.14203929901123, 6.0098490715026855, 8.206787109375, 8.827435493469238, 30.709091186523438, 33.27366638183594, 12.682785034179688, 12.329237937927246, 15.167587280273438, 4.973763465881348, 21.60417938232422, 16.689300537109375, 15.857894897460938, 19.311309814453125, 8.685699462890625, 35.818939208984375, 33.98244857788086, 17.68620491027832, 9.679377555847168, 7.5128173828125, 10.723532676696777, 6.190361022949219, 28.398475646972656, 20.789403915405273, 15.037062644958496, 17.627649307250977, 11.053919792175293, 10.827109336853027, 21.1890869140625, 6.274127006530762, 18.497669219970703, 50.9251708984375, 33.26618957519531, 28.658103942871094, 30.1602783203125, 33.99403381347656, 13.1170654296875, 5.993139743804932, 25.11739158630371, 8.449005126953125, 21.47747802734375, 17.201963424682617, 35.39588928222656, 5.251190185546875, 16.56024169921875, 27.721567153930664, 9.105286598205566, 36.1834716796875, 29.639633178710938, 14.537200927734375, 6.0017547607421875, 5.453071117401123, 8.211654663085938, 13.32562255859375, 22.979753494262695, 23.832199096679688, 25.87965202331543, 19.493303298950195, 10.890060424804688, 9.115142822265625, 20.57390022277832, 16.15475082397461, 9.702856063842773, 22.23811149597168, 9.732963562011719, 14.940644264221191, 6.364593505859375, 1.347198247909546, 1.913690447807312, 2.06172776222229, 2.699603796005249, 1.1461260318756104, 2.4514482021331787, 1.9072339534759521, 2.4772486686706543, 2.3696401119232178, 1.455794334411621, 1.8424309492111206, 0.9515790939331055, 1.5046567916870117, 1.2221025228500366, 1.9097557067871094, 0.8943449854850769, 1.4515403509140015, 1.6245298385620117, 2.629605770111084, 1.8301628828048706, 2.2194340229034424, 2.013157844543457, 1.3909597396850586, 1.0554494857788086, 1.293654441833496, 2.8108341693878174, 2.8437447547912598, 2.0693199634552, 2.0385560989379883, 1.5329608917236328, 2.4765543937683105, 1.012715458869934, 2.6612496376037598, 2.0169570446014404, 2.94846773147583, 1.8013299703598022, 2.8076906204223633, 0.9224076867103577, 2.1541173458099365, 1.4189281463623047, 2.7398734092712402, 1.5484206676483154, 1.9951318502426147, 1.108460783958435, 2.028536558151245, 1.737290620803833, 1.7771999835968018, 1.4712990522384644, 1.6764870882034302, 1.5981359481811523, 1.9639830589294434, 1.894619345664978, 0.8171815276145935, 1.501185417175293, 1.7441129684448242, 1.2674378156661987, 1.287841796875, 0.8033782243728638, 2.6730852127075195, 1.2671897411346436, 1.7507659196853638, 1.9722487926483154, 2.7904393672943115, 2.2717092037200928, 0.22643016278743744, 1.8591222763061523, 0.9603452682495117, 0.9079599380493164, 0.9732871651649475, 1.7620497941970825, 1.2161980867385864, 1.705872654914856, 1.1744357347488403, 1.3701395988464355, 1.9963483810424805, 2.182088613510132, 1.2188303470611572, 1.746180534362793, 2.3871679306030273, 1.7665094137191772, 2.1226613521575928, 2.065655469894409, 1.4279628992080688, 1.422688364982605, 1.733012080192566, 1.9125547409057617, 2.6711666584014893, 2.002479314804077, 1.7144631147384644, 1.124184489250183, 2.375741720199585, 0.8966493010520935, 1.525978922843933, 1.5775545835494995, 1.740077018737793, 2.277390480041504, 1.2028268575668335, 2.185185670852661, 1.9140938520431519, 2.0821008682250977, 1.8707760572433472, 1.5979009866714478, 2.8116235733032227, 1.201552391052246, 1.166005253791809, 1.933491587638855, 1.8159747123718262, 1.8486956357955933, 1.948097825050354, 2.042691230773926, 1.4066933393478394, 1.6315892934799194, 1.3010122776031494, 1.2401131391525269, 1.4473676681518555, 2.3511695861816406, 2.288578987121582, 2.1143598556518555, 1.3116189241409302, 1.7298349142074585, 1.0724363327026367, 0.9051753282546997, 1.1498804092407227, 1.361978530883789, 1.5422124862670898, 1.8547905683517456, 1.65412437915802, 2.231186866760254, 1.7331349849700928, 1.7689275741577148, 1.3186538219451904, 1.5177602767944336, 2.065002918243408, 1.7591601610183716, 1.5814554691314697, 2.4848473072052, 2.0544395446777344, 1.6426843404769897, 0.8438901901245117, 3.0595614910125732, 1.581720232963562, 1.7802523374557495, 9.5367431640625e-07, 2.1778323650360107, 0.7774879336357117, 2.2338767051696777, 2.2127530574798584, 2.020946502685547, 0.960293710231781, 1.4804750680923462, 1.227913737297058, 2.0137321949005127, 1.826289176940918, 1.5230462551116943, 1.3872958421707153, 0.9714059233665466, 2.5842647552490234, 2.0189297199249268, 2.4924120903015137, 2.611619234085083, 1.35673987865448, 2.0166468620300293, 3.268400192260742, 0.9212408065795898, 1.426259160041809, 1.914197325706482, 2.564680814743042, 2.634429931640625, 1.6103218793869019, 2.2884843349456787, 1.4727544784545898, 2.5402579307556152, 1.9094407558441162, 1.9369313716888428, 1.5485390424728394, 2.003784418106079, 2.3352880477905273, 2.159505605697632, 1.1640523672103882, 2.108146905899048, 9.5367431640625e-07, 0.654932975769043, 1.4579476118087769, 2.346597194671631, 1.773844599723816, 2.679936408996582, 2.14107608795166, 1.2653474807739258, 1.379481315612793, 1.8624314069747925, 1.0682653188705444, 1.6325559616088867, 1.244648814201355, 1.295795202255249, 0.09933948516845703, 1.3061132431030273, 1.999833345413208, 1.1139880418777466, 1.5893480777740479, 1.9016146659851074, 1.428589940071106, 1.9926338195800781, 1.0490903854370117, 1.9179105758666992, 1.43950355052948, 1.2578237056732178, 1.6422587633132935, 2.004805564880371, 1.4953659772872925, 2.6335089206695557, 2.56282901763916, 1.8856250047683716, 1.4511833190917969, 2.0231785774230957, 1.8585556745529175, 2.054055690765381, 1.5327672958374023, 1.5967270135879517, 1.169771432876587, 2.023564338684082, 1.5356206893920898, 1.5415258407592773, 1.4651943445205688, 1.2522324323654175, 1.2209023237228394, 2.062924385070801, 1.8576552867889404, 2.199009895324707, 2.5475587844848633, 2.0960805416107178, 1.5989786386489868, 2.0013790130615234, 1.2661224603652954, 1.9263105392456055, 2.240540027618408, 1.3312978744506836, 1.1911957263946533, 0.9430532455444336, 1.8239095211029053, 2.860295295715332, 2.315415382385254, 1.8413076400756836, 1.9015053510665894, 1.432673454284668, 1.1541069746017456, 1.6045951843261719, 2.0470874309539795, 1.460361123085022, 1.0686602592468262, 1.7585432529449463, 2.2600107192993164, 2.3413994312286377, 2.043196678161621, 9.5367431640625e-07, 2.176194190979004, 1.964180827140808, 1.645809292793274, 1.6951208114624023, 1.2627314329147339, 1.5699682235717773, 1.974934458732605, 1.982898235321045, 1.9876689910888672, 2.071242332458496, 1.7443456649780273, 0.8997889757156372, 1.5750092267990112, 1.3528552055358887, 1.5284020900726318, 1.2629661560058594, 1.9175080060958862, 2.5240821838378906, 9.5367431640625e-07, 2.9794323444366455, 1.5544511079788208, 2.7421746253967285, 1.7665966749191284, 0.8923503160476685, 1.6718554496765137, 1.2909116744995117, 1.5558347702026367, 0.906224250793457, 1.4134328365325928, 1.4583959579467773, 1.3780698776245117, 1.3870115280151367, 1.9862886667251587, 1.4554073810577393, 3.0922787189483643, 1.4060859680175781, 1.9069286584854126, 2.1218786239624023, 2.2670326232910156, 1.773801326751709, 2.218158483505249, 1.21626877784729, 1.9809008836746216, 2.029602527618408, 2.029712438583374, 0.9148568511009216, 0.08686696738004684, 0.01737111806869507, 0.025827616453170776, 0.06861519813537598, 0.004624068737030029, 0.011515210382640362, 0.03133755922317505, 0.07945448905229568, 0.0074759721755981445, 0.06797390431165695, 0.035296522080898285, 0.026197614148259163, 0.01755918748676777, 0.10456211864948273, 0.0066316756419837475, 0.10132955014705658, 0.0006620305357500911, 0.04570680484175682, 0.04793304204940796, 0.005511641502380371, 0.10125082731246948, 0.0, 0.06902184337377548, 0.002880755579099059, 0.0032913482282310724, 0.06438633054494858, 0.04714446887373924, 0.023130428045988083, 0.006497686728835106, 0.09920407831668854, 0.015011988580226898, 0.059417519718408585, 0.017295029014348984, 0.05994916707277298, 0.07256396859884262, 0.008550968952476978, 0.07942038029432297, 0.009825539775192738, 0.0360335111618042, 0.06707873195409775, 0.038495488464832306, 0.03846561908721924, 0.0008207559585571289, 0.008529206737875938, 0.04515862464904785, 0.041957318782806396, 0.040202319622039795, 0.04301190376281738, 0.06336169689893723, 0.08596563339233398, 0.029517829418182373, 0.05767391249537468, 0.04237610101699829, 5.118012268212624e-05, 0.04298131540417671, 0.007983913645148277, 0.061680831015110016, 0.09354465454816818, 0.05405579134821892, 0.06421689689159393, 0.02842630073428154, 0.043074190616607666, 0.019613470882177353, 0.06370562314987183, 0.0031214540358632803, 0.0, 0.054025229066610336, 0.05731701850891113, 0.030600372701883316, 0.01139161642640829, 0.012525015510618687, 0.00783617328852415, 0.048749398440122604, 0.055027369409799576, 0.006630184128880501, 0.0030469964258372784, 0.049291666597127914, 0.07902143895626068, 0.054950714111328125, 0.10194356739521027, 0.00040137767791748047, 0.00010420143371447921, 0.06616608798503876, 0.016196202486753464, 0.0416378378868103, 0.033680666238069534, 0.09151643514633179, 0.029415905475616455, 0.05271739885210991, 0.0011686705984175205, 0.0, 0.029871705919504166, 0.14142173528671265, 0.09344995021820068, 0.032485269010066986, 0.019299350678920746, 0.048792243003845215, 0.0024495618417859077, 0.04874873161315918, 0.027882609516382217, 0.027137108147144318, 0.02992585115134716, 0.05042887479066849, 0.043291471898555756, 0.04933224618434906, 0.0, 0.026226069778203964, 0.05037171393632889, 0.035971641540527344, 0.030267156660556793, 0.05948402360081673, 0.07160959392786026, 0.10515369474887848, 0.017703257501125336, 0.01579119637608528, 0.01115697342902422, 0.02001570723950863, 0.0498347282409668, 0.07356734573841095, 0.05655461177229881, 0.03135180100798607, 0.06937950104475021, 0.03930613771080971, 0.005827340297400951, 0.013869227841496468, 0.033899154514074326, 0.029544780030846596, 0.049925461411476135, 0.0030307620763778687, 0.018252916634082794, 0.03846585750579834, 0.014577405527234077, 0.03493374586105347, 0.043341994285583496, 0.03807926923036575, 0.03815557435154915, 1.7881393032936899e-09, 0.04344315454363823, 0.020854081958532333, 0.07548053562641144, 0.002230210928246379, 0.08715637773275375, 0.08382659405469894, 0.01059604063630104, 0.029325328767299652, 0.03135497868061066, 0.000840960128698498, 0.054563816636800766, 0.032724592834711075, 0.004058328922837973, 0.010075537487864494, 0.007105179131031036, 0.04044473171234131, 0.014960052445530891, 0.0023531215265393257, 0.032261550426483154, 0.07774835079908371, 0.040312107652425766, 0.03133755922317505, 0.005363113712519407, 0.042852114886045456, 0.029695451259613037, 0.08646845817565918, 0.019212448969483376, 0.06067795678973198, 0.030398063361644745, 0.059295911341905594, 0.02723078615963459, 1.19209286886246e-09, 5.9604643443123e-10, 0.09798553586006165, 0.0, 0.03923402726650238, 0.015064939856529236, 0.0242361631244421, 0.0, 0.003379643429070711, 0.017598090693354607, 0.049835748970508575, 1.4901161193847656e-06, 0.00042692184797488153, 0.04128655791282654, 0.09340106695890427, 0.015743913128972054, 0.0378258042037487, 0.029752526432275772, 0.02421899326145649, 0.02993423119187355, 0.031725648790597916, 0.05901403725147247, 0.02442246861755848, 0.024197446182370186, 0.026037782430648804, 0.04398136958479881, 0.0382542610168457, 0.05952220782637596, 0.0032706009224057198, 0.07951188087463379, 0.0004927515983581543, 0.04057764261960983, 0.03133755922317505, 0.028355959802865982, 0.03320830315351486, 0.0003276848583482206, 0.09814687818288803, 0.041628122329711914, 0.019701480865478516, 0.025113321840763092, 0.017320550978183746, 0.0073059797286987305, 0.05529302358627319, 0.005674597341567278, 0.08865640312433243, 0.0701543390750885, 0.02257072925567627, 0.04967833310365677, 0.05389753356575966, 0.013731267303228378, 0.0358736515045166, 0.07139849662780762, 0.10680360347032547, 0.03340883553028107, 0.047485627233982086, 0.09453853219747543, 0.09485367685556412, 0.10407865047454834, 0.02432536520063877, 0.08692636340856552, 0.08014003932476044, 0.14811328053474426, 0.001497507095336914, 0.05962955206632614, 0.06228327751159668, 0.03421070799231529, 0.019131723791360855, 0.08373674005270004, 0.07059741020202637, 0.09055805206298828, 0.09759431332349777, 0.05604499578475952, 0.07998848706483841, 0.04540038853883743, 0.09460687637329102, 0.023404980078339577, 0.03133755922317505, 0.026722747832536697, 0.03339850902557373, 0.0016718506813049316, 0.034951865673065186, 0.05634167417883873, 0.05938700959086418, 0.1346181035041809, 0.014670610427856445, 0.0003586614038795233, 0.002615883946418762, 0.03267500549554825, 0.0007590221939608455, 0.0693884938955307, 0.07748745381832123, 0.02429347299039364, 8.940696716308594e-07, 0.03133755922317505, 0.02343130111694336, 0.0, 0.0708322525024414, 0.06828372925519943, 0.061368510127067566, 0.03825738653540611, 0.011598744429647923, 0.0036374449264258146, 4.172325152040912e-09, 0.046098608523607254, 0.005195611156523228, 0.04148447513580322, 0.035920821130275726, 0.0498347282409668, 0.03912097215652466, 0.024041518568992615, 0.04180174693465233, 0.03904139995574951, 0.046213459223508835, 0.04466492682695389, 0.030347168445587158, 0.0517500564455986, 0.0, 0.028721068054437637, 0.009422898292541504, 0.04338140785694122, 0.025475570932030678, 0.044074755162000656, 0.03277834504842758, 0.05529302358627319, 0.04164952039718628, 0.12819212675094604, 0.009813542477786541, 0.014005371369421482, 0.0018501824233680964, 0.053976304829120636, 0.014781586825847626, 0.041524071246385574, 0.09094873070716858, 0.6525121927261353, 0.5348082780838013, 0.37490639090538025, 0.33464324474334717, 0.1831250935792923, 0.08872063457965851, 0.30648279190063477, 0.29208800196647644, 0.07858802378177643, 0.23502002656459808, 0.48068082332611084, 0.20876799523830414, 0.0033808117732405663, 0.22026105225086212, 0.3144373893737793, 0.2109220027923584, 0.37951430678367615, 0.09689582884311676, 0.6344106793403625, 0.43671801686286926, 0.11030548810958862, 0.3181070387363434, 0.21318112313747406, 0.2968370318412781, 0.28846508264541626, 0.3692730963230133, 0.307709276676178, 0.09397810697555542, 0.07727593928575516, 0.34301838278770447, 0.44875049591064453, 0.19925574958324432, 0.20781734585762024, 0.3479250371456146, 0.3513689637184143, 0.381142258644104, 0.18185904622077942, 0.12461134791374207, 0.35415464639663696, 0.1834072321653366, 0.38434654474258423, 0.20628876984119415, 0.15412433445453644, 0.08641166239976883, 0.2739866077899933, 0.09159880131483078, 0.344445139169693, 0.30694374442100525, 0.10420083999633789, 0.09690534323453903, 0.1683000773191452, 0.28001898527145386, 0.31678950786590576, 0.23020406067371368, 0.6666267514228821, 0.1913643181324005, 0.5000461339950562, 0.09582667797803879, 0.4390920102596283, 0.4426896572113037, 0.21345344185829163, 0.4416622817516327, 0.2508883476257324, 0.23852817714214325, 0.4053536057472229, 0.3489438593387604, 0.4201362133026123, 0.33513885736465454, 0.22905199229717255, 0.2482784241437912, 0.16698020696640015, 0.2122688591480255, 0.21328753232955933, 0.19982749223709106, 0.3101743757724762, 0.08205278217792511, 0.4946620762348175, 0.12995749711990356, 0.28216612339019775, 0.37008196115493774, 0.3196846842765808, 0.17628051340579987, 0.1908539980649948, 9.01848979992792e-05, 0.3583451807498932, 0.30929964780807495, 0.11798054724931717, 0.08904089033603668, 0.3186682164669037, 0.011482331901788712, 0.011167054064571857, 0.15746456384658813, 0.4281326234340668, 0.13012051582336426, 0.24770084023475647, 0.3761856257915497, 0.2338315099477768, 0.04378075525164604, 0.056753624230623245, 0.4501892626285553, 0.39785274863243103, 0.3565690517425537, 0.1549181491136551, 0.08777663856744766, 0.34140557050704956, 0.025859585031867027, 0.3891499936580658, 0.11663632839918137, 0.21853557229042053, 0.5521265864372253, 0.16405993700027466, 0.24665427207946777, 0.34856104850769043, 0.3852223753929138, 0.22014063596725464, 0.21357674896717072, 0.22400164604187012, 0.3840126097202301, 0.10980607569217682, 0.4957691729068756, 0.4459548890590668, 0.38752052187919617, 0.20674851536750793, 0.18186591565608978, 0.37198135256767273, 0.09761041402816772, 0.30018046498298645, 0.28780046105384827, 0.27751657366752625, 0.302348256111145, 0.1052333265542984, 0.3700481355190277, 0.10048697143793106, 0.1461799144744873, 0.19155141711235046, 0.09621402621269226, 0.5566079616546631, 0.42796531319618225, 0.5867836475372314, 0.010975492186844349, 0.20172767341136932, 0.2707609534263611, 0.45955145359039307, 0.4699710011482239, 0.2699483036994934, 0.34507307410240173, 0.00018429507326800376, 0.24283547699451447, 0.2402634173631668, 0.11060052365064621, 0.2269493192434311, 0.11796852201223373, 0.46533849835395813, 0.4089220464229584, 0.20961661636829376, 0.12058672308921814, 0.16148988902568817, 0.07119302451610565, 0.23780253529548645, 0.19541434943675995, 0.21460337936878204, 0.13166435062885284, 0.3904869258403778, 0.1862640380859375, 0.3455953598022461, 0.1800057590007782, 0.23318889737129211, 0.2739948630332947, 0.34638911485671997, 0.47306543588638306, 0.1396857649087906, 0.16955910623073578, 0.3807711601257324, 0.2821013927459717, 0.26761728525161743, 0.1667346954345703, 0.48541712760925293, 0.10636333376169205, 0.1775962859392166, 0.18239842355251312, 0.27078977227211, 0.3225235044956207, 0.30663394927978516, 0.17344720661640167, 0.24289119243621826, 0.08875619620084763, 0.3437127470970154, 0.005720857065171003, 0.19256936013698578, 0.3681316673755646, 0.24947474896907806, 0.08386938273906708, 0.2338687777519226, 0.42593684792518616, 0.281084805727005, 0.21692311763763428, 0.10808806866407394, 0.2345457822084427, 0.47587519884109497, 0.30448296666145325, 7.596096603286473e-15, 0.3082544505596161, 0.20801027119159698, 0.09636781364679337, 0.34384146332740784, 0.31554874777793884, 0.10081716626882553, 0.31653088331222534, 0.11299686878919601, 0.17713557183742523, 0.35044118762016296, 0.23389843106269836, 0.3268810212612152, 0.28023970127105713, 0.16057364642620087, 0.19982664287090302, 0.3571279048919678, 0.3348979353904724, 0.12377777695655823, 0.3726229667663574, 0.09622127562761307, 0.3852607309818268, 0.4366116225719452, 0.33020877838134766, 0.26601576805114746, 0.2631568908691406, 0.17820222675800323, 0.3931557238101959, 0.2380828559398651, 0.4402099549770355, 0.1840873509645462, 0.3869500756263733, 0.3185090124607086, 0.23588311672210693, 0.10179765522480011, 0.18706552684307098, 0.2242099642753601, 0.3387308120727539, 0.11143287271261215, 0.13030561804771423, 0.15546171367168427, 0.3199094831943512, 0.46583491563796997, 0.34605491161346436, 0.18280871212482452, 0.17110656201839447, 0.33432865142822266, 0.1577598750591278, 0.1458873152732849, 0.4272196888923645, 0.3412794768810272, 0.28067269921302795, 0.09512878954410553, 0.19073544442653656, 0.21431903541088104, 0.2028321474790573, 0.20555812120437622, 0.5334612727165222, 0.3539239466190338, 0.18710008263587952, 0.34569525718688965, 0.2727004885673523, 0.32271942496299744, 0.4352211654186249, 0.23964636027812958, 0.16595855355262756, 0.3276631236076355, 0.1833982616662979, 0.07788544148206711, 0.4660363793373108, 0.17206570506095886, 0.2132381647825241, 0.3427431285381317, 0.010035663843154907, 0.005119153764098883, 0.31190812587738037, 0.2542876899242401, 0.6278822422027588, 0.2721661329269409, 0.10075260698795319, 0.31048133969306946, 0.32488104701042175, 0.3306821286678314, 0.12646612524986267, 0.3072458803653717, 1.2809053303978763e-14, 0.3080907464027405, 0.18032531440258026, 0.1257399171590805, 0.11649167537689209, 0.4443640112876892, 0.08629956841468811, 0.0900501012802124, 0.29366403818130493, 0.10153022408485413, 0.1366361826658249, 0.37971168756484985, 0.26665666699409485, 0.08126229792833328, 57.00675582885742, 14.346099853515625, 48.56947326660156, 14.898320198059082, 7.5914764404296875, 8.539093971252441, 8.056976318359375, 35.52806091308594, 12.415771484375, 14.574538230895996, 10.999076843261719, 20.05604362487793, 32.54353332519531, 4.5444769859313965, 5.222038269042969, 57.022705078125, 22.65461540222168, 3.536376953125, 9.313228607177734, 9.724029541015625, 6.415037631988525, 27.0246524810791, 7.224365234375, 13.099138259887695, 43.76722717285156, 23.225038528442383, 19.17665672302246, 32.442787170410156, 15.5391845703125, 42.851356506347656, 30.03558349609375, 10.876809120178223, 9.442153930664062, 29.24642562866211, 18.56682014465332, 13.23297119140625, 10.684600830078125, 17.131988525390625, 21.99848747253418, 18.88618278503418, 16.16224479675293, 7.984663009643555, 18.599241256713867, 52.483154296875, 87.78878784179688, 31.650741577148438, 13.743804931640625, 9.53741455078125, 14.184971809387207, 13.466781616210938, 17.215782165527344, 7.084174633026123, 11.50631332397461, 20.84451675415039, 17.26617431640625, 25.69990348815918, 20.604154586791992, 19.74128532409668, 22.706254959106445, 16.893667221069336, 10.577580451965332, 33.99481201171875, 30.243837356567383, 30.306869506835938, 21.93292236328125, 10.264493942260742, 20.814931869506836, 9.411041259765625, 17.316532135009766, 14.01402759552002, 11.15719985961914, 20.922332763671875, 8.478378295898438, 13.0250244140625, 24.186683654785156, 11.699920654296875, 8.197189331054688, 12.444747924804688, 24.013391494750977, 51.307861328125, 6.04332971572876, 52.047420501708984, 24.53203582763672, 16.815202713012695, 25.102121353149414, 5.7220001220703125, 38.47658920288086, 19.67498016357422, 12.083818435668945, 20.92841339111328, 6.995204925537109, 19.47767448425293, 7.6112823486328125, 15.077255249023438, 11.197768211364746, 11.967565536499023, 22.52760124206543, 47.72159957885742, 29.413963317871094, 30.213836669921875, 37.65320587158203, 7.136383056640625, 5.788190841674805, 9.44287109375, 27.343719482421875, 23.441423416137695, 16.376758575439453, 11.11651611328125, 6.265235424041748, 30.830810546875, 35.57632827758789, 31.429105758666992, 15.283220291137695, 21.904525756835938, 10.667098999023438, 28.491605758666992, 4.968571186065674, 28.890199661254883, 13.784408569335938, 16.95814323425293, 7.393365383148193, 10.978737831115723, 37.25318908691406, 46.545711517333984, 33.9322395324707, 57.98936462402344, 18.040945053100586, 13.283888816833496, 24.243331909179688, 8.16229248046875, 23.38045310974121, 34.85359191894531, 13.641571044921875, 4.6394195556640625, 33.056243896484375, 37.4542236328125, 27.233016967773438, 35.80755615234375, 9.486149787902832, 23.469486236572266, 19.53968620300293, 15.532443046569824, 23.629318237304688, 26.853368759155273, 59.17324447631836, 19.721343994140625, 22.779191970825195, 59.33164978027344, 24.041112899780273, 8.810199737548828, 14.010465621948242, 45.821449279785156, 10.8140869140625, 13.016554832458496, 22.132604598999023, 7.022287368774414, 21.833251953125, 9.268921852111816, 8.617202758789062, 17.35455322265625, 15.819384574890137, 24.65937614440918, 41.83376693725586, 81.48159790039062, 44.13307571411133, 18.27040672302246, 30.71758460998535, 8.998565673828125, 13.106124877929688, 13.753952026367188, 32.20301818847656, 17.58648681640625, 10.355464935302734, 16.267242431640625, 8.944854736328125, 16.698890686035156, 33.18701171875, 23.506032943725586, 12.87644100189209, 19.5101318359375, 6.966280937194824, 14.927642822265625, 7.5781097412109375, 20.49200439453125, 24.046478271484375, 47.80839920043945, 42.688232421875, 10.266005516052246, 11.791831016540527, 10.575227737426758, 37.031700134277344, 9.357757568359375, 48.6636962890625, 3.081787109375, 26.432174682617188, 66.7059326171875, 25.187835693359375, 35.04331970214844, 27.70118522644043, 7.405932426452637, 32.7645263671875, 17.72834587097168, 72.08568572998047, 16.701629638671875, 28.74150848388672, 112.86820220947266, 33.605926513671875, 24.867679595947266, 54.2464485168457, 15.399847984313965, 35.874298095703125, 25.555831909179688, 18.363418579101562, 19.31181526184082, 54.46917724609375, 4.918952941894531, 54.42610168457031, 66.85575866699219, 12.7823486328125, 58.45229721069336, 26.5672550201416, 12.15631103515625, 9.123421669006348, 17.98478889465332, 17.20391845703125, 12.295516967773438, 14.6466064453125, 25.092538833618164, 16.781784057617188, 21.61604118347168, 37.45380783081055, 6.626489639282227, 16.97705078125, 17.708698272705078, 22.180709838867188, 49.46238327026367, 25.73383903503418, 16.77891731262207, 26.6871337890625, 10.706867218017578, 31.71571159362793, 16.720504760742188, 29.13960075378418, 27.31964111328125, 14.391435623168945, 41.93217849731445, 14.768190383911133, 21.522611618041992, 10.603583335876465, 17.028331756591797, 8.379745483398438, 9.054238319396973, 57.90260696411133, 11.215354919433594, 20.68538475036621, 25.20307731628418, 7.17108154296875, 37.46317672729492, 7.732300281524658, 17.83460235595703, 22.237455368041992, 6.040557861328125, 44.45901107788086, 35.67131042480469, 58.38199996948242, 14.954543113708496, 9.979476928710938, 36.73090744018555, 22.738082885742188, 14.630477905273438, 22.761459350585938, 20.4263916015625, 6.128326416015625, 9.745933532714844, 9.992692947387695, 8.331101417541504, 10.843791007995605, 7.853515625, 9.368057250976562, 28.90802001953125, 7.34808349609375, 7.262272834777832, 8.548919677734375, 31.408737182617188, 14.181243896484375, 7.158111572265625, 20.20733642578125, 16.431365966796875, 14.765761375427246, 39.47825241088867, 16.13587188720703, 18.563600540161133, 9.323501586914062, 10.2288818359375, 23.529098510742188, 21.316650390625, 14.382643699645996, 51.65394592285156, 11.328619956970215, 10.204727172851562, 2.2908620834350586, 1.8201377391815186, 2.445086717605591, 2.041031837463379, 1.281166911125183, 1.3543272018432617, 0.9834718108177185, 1.346134901046753, 1.3939622640609741, 2.0728883743286133, 1.7231931686401367, 1.8028725385665894, 1.436775803565979, 2.035762071609497, 1.4849976301193237, 1.7490700483322144, 1.927651286125183, 1.3702285289764404, 1.0936449766159058, 1.4596357345581055, 1.6886816024780273, 1.2281845808029175, 1.672224998474121, 1.483576774597168, 2.1596620082855225, 1.0777456760406494, 1.9723535776138306, 1.9322794675827026, 2.1877622604370117, 2.9720280170440674, 1.5476473569869995, 1.6417587995529175, 0.9451925158500671, 1.895493984222412, 1.3657963275909424, 0.0575152188539505, 1.6489753723144531, 1.6799273490905762, 1.3369600772857666, 1.2397164106369019, 1.9770234823226929, 1.6674102544784546, 1.7961721420288086, 1.8809808492660522, 2.400569438934326, 3.1189587116241455, 2.2968380451202393, 1.9551409482955933, 2.3021230697631836, 2.488673448562622, 1.9138308763504028, 1.8777689933776855, 2.0817747116088867, 0.12610435485839844, 1.1538208723068237, 1.5885429382324219, 2.2967982292175293, 1.4433786869049072, 2.5265722274780273, 1.7601770162582397, 9.5367431640625e-07, 1.9154975414276123, 1.608270525932312, 1.6107935905456543, 2.30686354637146, 1.0862507820129395, 1.90407133102417, 2.3482844829559326, 2.285930633544922, 2.8982951641082764, 9.5367431640625e-07, 1.8450363874435425, 1.6461347341537476, 2.096872091293335, 1.4983001947402954, 1.3656110763549805, 2.175909996032715, 2.0407750606536865, 0.7398900985717773, 1.810774803161621, 2.201061248779297, 1.672656774520874, 1.945643424987793, 2.1014137268066406, 2.5873656272888184, 2.241860866546631, 1.6752691268920898, 0.6143598556518555, 1.5581711530685425, 1.907570719718933, 2.9749395847320557, 1.3354568481445312, 1.0525426864624023, 1.9746625423431396, 2.942667245864868, 1.2485977411270142, 1.812563180923462, 1.9617615938186646, 2.228695869445801, 1.3124674558639526, 1.7370988130569458, 1.2414655685424805, 2.783982515335083, 2.9810192584991455, 1.9572315216064453, 2.1620988845825195, 2.574652671813965, 9.5367431640625e-07, 2.6338038444519043, 9.5367431640625e-07, 2.1650619506835938, 1.1279534101486206, 0.942561149597168, 1.082503318786621, 1.7684595584869385, 1.189047932624817, 1.8059706687927246, 1.6046496629714966, 1.889451265335083, 1.3356361389160156, 9.5367431640625e-07, 1.2342214584350586, 1.9240527153015137, 2.1050920486450195, 1.9173061847686768, 1.758906364440918, 1.9534101486206055, 1.8673244714736938, 1.5265884399414062, 2.301267147064209, 2.50825834274292, 2.5490267276763916, 2.440423011779785, 2.7387635707855225, 2.1600489616394043, 1.0972557067871094, 1.4028911590576172, 1.7747429609298706, 1.7400197982788086, 2.084977626800537, 1.910780906677246, 2.019001007080078, 2.3174381256103516, 1.3396538496017456, 1.8512619733810425, 1.5163286924362183, 2.4699182510375977, 1.3750877380371094, 0.996762216091156, 1.5834401845932007, 1.8449982404708862, 1.9499869346618652, 1.8765286207199097, 1.0199793577194214, 1.317283034324646, 1.1728878021240234, 2.4416680335998535, 2.042668104171753, 3.0942888259887695, 1.854624629020691, 1.74294912815094, 2.9818661212921143, 1.3524198532104492, 1.7260618209838867, 1.5136370658874512, 1.8370755910873413, 1.916193962097168, 1.1533325910568237, 1.6329411268234253, 1.6448392868041992, 1.2037036418914795, 1.1626510620117188, 1.7289330959320068, 1.6314362287521362, 1.6433991193771362, 1.6031179428100586, 2.5276689529418945, 2.1609315872192383, 1.3521413803100586, 2.5711865425109863, 1.141311764717102, 3.191693067550659, 2.092369794845581, 1.374015212059021, 0.4212942123413086, 1.761988639831543, 1.5106191635131836, 2.268479347229004, 1.253395915031433, 1.196747899055481, 1.5985289812088013, 0.8930082321166992, 2.0895376205444336, 1.8037313222885132, 2.1113812923431396, 2.5573015213012695, 1.8864198923110962, 2.0625662803649902, 1.86830735206604, 2.5606377124786377, 2.098555326461792, 1.5692434310913086, 2.9161999225616455, 1.31344735622406, 2.5819990634918213, 1.7488834857940674, 2.254185676574707, 1.691219449043274, 1.7357364892959595, 9.5367431640625e-07, 1.4918062686920166, 1.4538614749908447, 1.9791975021362305, 1.7363022565841675, 1.2404183149337769, 0.8251142501831055, 0.9323357939720154, 1.6062960624694824, 1.9845571517944336, 1.3155893087387085, 1.8881258964538574, 1.942940592765808, 1.9729812145233154, 0.7395162582397461, 1.5987862348556519, 1.2383915185928345, 2.2236857414245605, 1.9401971101760864, 2.062836170196533, 2.2233896255493164, 2.1446943283081055, 2.731868267059326, 2.699671506881714, 2.2650461196899414, 0.6482305526733398, 1.8677927255630493, 1.3941503763198853, 0.8213506937026978, 0.6240377426147461, 1.1903650760650635, 0.08206207305192947, 1.2224129438400269, 2.609452247619629, 2.0868706703186035, 1.929842472076416, 1.9130672216415405, 1.7968358993530273, 2.0240254402160645, 1.5509477853775024, 1.972743034362793, 1.432338833808899, 2.2443759441375732, 2.963092088699341, 1.492699146270752, 2.046078681945801, 2.5096235275268555, 2.147315263748169, 1.5591024160385132, 1.9525421857833862, 2.127639055252075, 1.511340856552124, 1.6740689277648926, 1.6119184494018555, 0.6338472366333008, 1.0249464511871338, 1.1403924226760864, 1.2895421981811523, 1.7079038619995117, 1.7723760604858398, 1.4726463556289673, 2.1394362449645996, 1.734857439994812, 1.3749651908874512, 1.856416940689087, 0.9651309251785278, 1.0163383483886719, 2.5008492469787598, 1.1342382431030273, 1.9913915395736694, 1.9857664108276367, 2.1732592582702637, 2.117852210998535, 1.615071415901184, 1.8416565656661987, 3.590176820755005, 2.312713623046875, 1.0969228744506836, 1.698176383972168, 1.793274998664856, 1.5206785202026367, 2.1558351516723633, 1.2381923198699951, 2.4020161628723145, 1.7046211957931519, 1.631722092628479, 1.4041357040405273, 1.998537540435791, 1.8586513996124268, 1.6442480087280273, 1.4982086420059204, 0.051630791276693344, 0.06592655181884766, 0.024556299671530724, 0.04225212335586548, 0.03488404303789139, 0.030715441331267357, 4.397213342599571e-05, 0.0017150657949969172, 0.04633617401123047, 0.005861384328454733, 0.013301231898367405, 0.004736379720270634, 0.01569598913192749, 0.0031557679176330566, 0.0013742225710302591, 0.05660801753401756, 0.0667584165930748, 0.0773649662733078, 0.0, 0.08565780520439148, 0.03133755922317505, 0.006535583641380072, 0.11304349452257156, 0.042287129908800125, 0.03852621838450432, 0.0, 0.0027583371847867966, 0.04192784056067467, 0.08181627839803696, 0.029517829418182373, 0.13528043031692505, 0.027903933078050613, 0.05975816026329994, 0.03781318664550781, 0.04299056902527809, 0.007408684119582176, 0.05529302358627319, 0.059877265244722366, 0.07872388511896133, 0.021916961297392845, 0.07921898365020752, 0.08355586230754852, 0.030677122995257378, 0.03339850902557373, 0.014829342253506184, 0.0, 0.01828814297914505, 0.0029432219453155994, 0.02881813980638981, 0.015470790676772594, 0.0279618501663208, 0.06108521297574043, 0.011358804069459438, 0.0426667295396328, 0.0713089182972908, 0.06530845165252686, 0.10105184465646744, 0.08387154340744019, 0.059875696897506714, 0.10015752911567688, 0.015359403565526009, 0.04472756385803223, 0.038540810346603394, 0.09204971045255661, 0.004383157938718796, 0.051926806569099426, 0.003997584339231253, 3.409564305911772e-05, 0.12200683355331421, 0.019977835938334465, 0.06548452377319336, 0.07893157005310059, 0.0, 0.06510729342699051, 0.06050043925642967, 0.0, 0.021190941333770752, 2.9981134730405756e-07, 0.026819180697202682, 0.07458791136741638, 0.17885427176952362, 0.0737832635641098, 0.04310409352183342, 0.10442590713500977, 0.0372886061668396, 0.11029604077339172, 0.0034447545185685158, 0.0016009307000786066, 0.04314393922686577, 0.038639187812805176, 0.05277036875486374, 0.05216348543763161, 0.056443195790052414, 0.10060589760541916, 0.09301352500915527, 0.024079926311969757, 0.025624603033065796, 0.015108760446310043, 0.012590725906193256, 0.005745351780205965, 0.040547408163547516, 0.010663812048733234, 0.06530845165252686, 0.027899397537112236, 0.00259030400775373, 0.01925267092883587, 0.05531526356935501, 0.03661888837814331, 0.02789938449859619, 0.042713478207588196, 0.00025613067555241287, 0.03454441949725151, 0.06383523344993591, 0.024018025025725365, 0.03148782253265381, 0.015590966679155827, 0.05760401114821434, 0.03793336823582649, 0.10914603620767593, 0.030566303059458733, 0.1037677526473999, 0.03384534269571304, 0.05178696662187576, 0.0028440558817237616, 0.062396906316280365, 0.003693342674523592, 5.716204395866953e-05, 0.05836856737732887, 0.000413873785873875, 0.029447605833411217, 0.06212824583053589, 0.0005240720347501338, 0.0667940005660057, 0.07777447253465652, 0.035752177238464355, 0.07423688471317291, 0.014240860939025879, 0.01698371209204197, 0.05017179995775223, 0.08439408242702484, 0.05303497612476349, 0.03462880849838257, 0.014080535620450974, 0.03340594097971916, 0.08681993186473846, 0.0011299913749098778, 0.028040356934070587, 0.05984259024262428, 0.04905373603105545, 0.021113542839884758, 0.00744811212643981, 0.040382564067840576, 0.07059741020202637, 0.10199610143899918, 0.05872035771608353, 0.0001352012186544016, 0.0320747047662735, 0.017248861491680145, 0.12046032398939133, 0.004708047024905682, 0.008043233305215836, 0.0380653478205204, 0.029438495635986328, 0.01257283054292202, 0.009049961343407631, 0.04605276137590408, 0.018033821135759354, 0.0, 0.03163778781890869, 0.0319947674870491, 0.0878116562962532, 0.0498347282409668, 0.014790773391723633, 0.005985280033200979, 0.098654605448246, 0.053498703986406326, 0.0016210793983191252, 0.041628122329711914, 0.07840686291456223, 0.06401463598012924, 0.08716809749603271, 0.0, 0.07053954899311066, 0.013049125671386719, 0.011687756516039371, 0.0541607029736042, 0.062302470207214355, 0.007263369858264923, 0.004612327553331852, 6.644069799222052e-05, 0.06682151556015015, 0.0, 0.023554924875497818, 0.06836699694395065, 0.04058052599430084, 0.03390192985534668, 0.036922454833984375, 0.011697649955749512, 0.035930655896663666, 0.021391654387116432, 0.06266999244689941, 0.011994123458862305, 0.0005547404289245605, 0.050764475017786026, 0.07771993428468704, 0.0989568904042244, 0.009211553260684013, 0.02601395733654499, 0.07718140631914139, 0.08680617809295654, 0.04947547987103462, 0.045665569603443146, 0.08405232429504395, 0.04143913835287094, 0.033604081720113754, 0.027971230447292328, 0.07791537046432495, 0.08428800106048584, 0.055395472794771194, 0.013692989945411682, 0.08589029312133789, 0.05529157444834709, 8.497536327922717e-05, 0.053676486015319824, 0.011211685836315155, 0.00026846289983950555, 0.06365490704774857, 0.08142298460006714, 0.12718471884727478, 0.023140713572502136, 0.015459375455975533, 0.0029293925035744905, 0.0598328672349453, 0.02960943803191185, 0.027031945064663887, 0.003331762971356511, 0.07013559341430664, 0.048157546669244766, 0.05615765601396561, 0.07529649138450623, 0.06280476599931717, 3.188729169778526e-05, 0.06723912060260773, 0.035053789615631104, 0.07959678769111633, 0.0038292407989501953, 0.031425297260284424, 0.10117053985595703, 0.045956313610076904, 0.030863039195537567, 0.039905011653900146, 0.019530119374394417, 0.09076272696256638, 0.05529302358627319, 0.035322487354278564, 0.040295861661434174, 0.03224983066320419, 0.055342741310596466, 0.05404484644532204, 0.0721898227930069, 0.0929294154047966, 0.04028187692165375, 0.05942118167877197, 0.08118169009685516, 0.005272676702588797, 0.0, 0.050089091062545776, 0.04196178913116455, 0.08972890675067902, 0.0, 0.01827407069504261, 0.08188816159963608, 0.07837772369384766, 0.022232502698898315, 0.0012139850296080112, 0.07615378499031067, 0.039178576320409775, 0.056791648268699646, 0.09056459367275238, 0.009804069995880127, 0.0431751050055027, 0.031520139425992966, 0.06046868488192558, 0.04622020944952965, 0.07624142616987228, 0.09013276547193527, 0.01823492720723152, 0.0, 0.03046281263232231, 0.07167024165391922, 0.07744763046503067, 0.0498347282409668, 0.06320887804031372, 0.06626605242490768, 0.03336983546614647, 0.04241090640425682, 1.1920928955078125e-07, 0.0009163414943031967, 0.06058694049715996, 0.06940031051635742, 0.26204922795295715, 0.1955578625202179, 0.25084739923477173, 0.09431468695402145, 0.08283477276563644, 0.2858874201774597, 0.20757511258125305, 0.325590044260025, 0.24954631924629211, 0.20627456903457642, 0.3453969359397888, 0.15644454956054688, 0.35916388034820557, 0.221830815076828, 0.1034872904419899, 0.1498178094625473, 0.092262402176857, 0.35723501443862915, 0.23406413197517395, 0.2210547924041748, 0.09282507002353668, 0.23235122859477997, 0.27676069736480713, 0.22675257921218872, 0.2097959816455841, 0.2394494265317917, 0.2341015636920929, 0.3278723955154419, 0.3248244524002075, 0.0049724881537258625, 0.33033984899520874, 0.2276063710451126, 0.07708164304494858, 0.23316137492656708, 0.44842711091041565, 0.24649329483509064, 0.2578703761100769, 0.3443135619163513, 0.44389671087265015, 0.16596466302871704, 0.3330758512020111, 0.34470999240875244, 0.12535126507282257, 0.22368399798870087, 0.29661574959754944, 0.2705305516719818, 0.2833700478076935, 0.2566126883029938, 0.5714242458343506, 0.2711634337902069, 0.5815572142601013, 0.5693526864051819, 0.3840194642543793, 0.4704556167125702, 0.21899612247943878, 0.44985881447792053, 0.44577857851982117, 0.42445674538612366, 0.2680368423461914, 0.323808878660202, 0.3187599778175354, 0.211007222533226, 0.23033912479877472, 0.47763410210609436, 0.34088054299354553, 0.5791597366333008, 0.1666557490825653, 0.3358581066131592, 0.17806731164455414, 0.13819271326065063, 0.3915708065032959, 0.15651103854179382, 0.41814231872558594, 0.27792784571647644, 1.241249704202977e-14, 0.41248244047164917, 0.21903136372566223, 0.17545203864574432, 0.3274179697036743, 0.420698881149292, 0.4493212103843689, 0.46104320883750916, 0.39249587059020996, 0.27833670377731323, 0.3046332895755768, 0.08418434858322144, 0.2284294217824936, 0.23374775052070618, 0.22239428758621216, 0.1823519468307495, 0.2163110375404358, 0.35818496346473694, 0.2782312035560608, 0.5622727870941162, 0.29669272899627686, 0.569303035736084, 0.24279826879501343, 0.2116822749376297, 0.12194468080997467, 0.011678190901875496, 0.4976951777935028, 0.6134182810783386, 0.31684038043022156, 0.480823278427124, 0.21692578494548798, 0.2109549343585968, 0.23403429985046387, 0.23831088840961456, 0.2983388900756836, 0.4437403082847595, 0.46734100580215454, 0.3312337398529053, 0.4167005717754364, 0.5497158765792847, 0.2922372817993164, 0.2222278118133545, 0.20245879888534546, 0.3544398546218872, 0.4714716374874115, 0.34100618958473206, 0.08838186413049698, 0.28621387481689453, 0.16125304996967316, 0.3295137584209442, 0.3648996353149414, 0.1702093631029129, 0.2568451762199402, 0.3635856807231903, 0.3756025731563568, 0.2829698324203491, 0.5584142804145813, 0.39565497636795044, 0.20965610444545746, 0.22965632379055023, 0.4489874839782715, 0.2355656921863556, 0.4161031246185303, 0.18829387426376343, 0.5930112600326538, 0.11700538545846939, 0.20909720659255981, 0.576972246170044, 0.1657489687204361, 0.29385361075401306, 0.3025323152542114, 0.5138636827468872, 0.12638309597969055, 0.30929702520370483, 0.21828393638134003, 0.32849135994911194, 0.25321245193481445, 0.5837581753730774, 0.24066847562789917, 0.46311241388320923, 0.24710781872272491, 0.19092410802841187, 0.25121623277664185, 0.7111966013908386, 0.5284847021102905, 0.16221164166927338, 0.07673382759094238, 0.21125589311122894, 0.1647486388683319, 0.4186871349811554, 0.46494144201278687, 0.2671438753604889, 0.3162727952003479, 0.3890936076641083, 0.08990094810724258, 0.1632719188928604, 0.420912504196167, 0.44612693786621094, 0.26218584179878235, 0.19416482746601105, 0.23733322322368622, 0.5630919337272644, 0.4662204682826996, 0.5406331419944763, 0.3988422453403473, 0.2744431495666504, 0.34554171562194824, 0.3167248070240021, 0.40930095314979553, 0.11159580945968628, 0.3585023880004883, 0.5903218984603882, 0.10218260437250137, 0.2600865960121155, 0.1994837075471878, 0.11144989728927612, 0.27509090304374695, 0.18143081665039062, 0.2239660769701004, 0.316775918006897, 0.19329330325126648, 0.7715364694595337, 0.4607183039188385, 0.27833324670791626, 0.2956090569496155, 0.2572152018547058, 0.25791361927986145, 0.20188339054584503, 0.21580250561237335, 0.08657922595739365, 0.516627848148346, 0.21652863919734955, 0.16552157700061798, 0.4808046519756317, 0.13494974374771118, 0.40979430079460144, 0.5878027081489563, 0.5525026321411133, 0.32534220814704895, 0.49300646781921387, 0.15811428427696228, 0.3572036325931549, 0.3217020630836487, 0.13532496988773346, 0.415237158536911, 0.1075265109539032, 0.0898057222366333, 0.5547763109207153, 0.4318016767501831, 0.4059491753578186, 0.22874799370765686, 0.10283134132623672, 0.38099440932273865, 0.30963051319122314, 0.20105889439582825, 0.21025589108467102, 0.12565560638904572, 0.3547314703464508, 0.08841947466135025, 0.21489737927913666, 0.2636428773403168, 0.10594169050455093, 0.37515464425086975, 0.35466468334198, 0.18509402871131897, 0.517839252948761, 0.3099147081375122, 0.5642485022544861, 0.22897611558437347, 0.23068836331367493, 0.08939843624830246, 0.3765527904033661, 0.1987053006887436, 0.18975871801376343, 0.6835490465164185, 0.24249938130378723, 0.0038134960923343897, 0.5142654180526733, 0.47218117117881775, 0.18829333782196045, 0.3215924799442291, 0.2723446488380432, 0.08025214821100235, 0.3364301323890686, 0.08048133552074432, 0.397006094455719, 0.21778087317943573, 0.10948801040649414, 0.12641821801662445, 0.23520854115486145, 0.22679901123046875, 0.2841053605079651, 0.7100422978401184, 0.20797042548656464, 0.2995394468307495, 0.3375478982925415, 0.3427068293094635, 0.5338298082351685, 0.18586213886737823, 0.23148015141487122, 0.22351428866386414, 0.2539602816104889, 0.3000936806201935, 0.5727205276489258, 0.34047433733940125, 0.3302838206291199, 0.24386823177337646, 0.46009451150894165, 0.33432769775390625, 0.35547682642936707, 0.49644285440444946, 0.3693275451660156, 0.2920648455619812, 0.2691289782524109, 0.10831357538700104, 0.32114797830581665, 0.1598658561706543, 0.18024928867816925, 0.21682606637477875, 0.41039884090423584, 0.21518343687057495, 0.22752025723457336, 0.31408822536468506, 0.1890268325805664, 0.16958625614643097, 0.3743734359741211, 33.34330368041992, 33.64796447753906, 10.051712036132812, 28.98060417175293, 64.0591812133789, 67.55233764648438, 16.400680541992188, 29.79117202758789, 23.334884643554688, 55.895599365234375, 22.540863037109375, 45.04423904418945, 25.4013671875, 10.01967716217041, 33.30241394042969, 14.828948974609375, 14.0916109085083, 26.136259078979492, 38.27777099609375, 11.075881004333496, 42.73323059082031, 14.002548217773438, 13.081708908081055, 9.918930053710938, 25.17427635192871, 44.983978271484375, 10.416215896606445, 10.545961380004883, 17.42652702331543, 18.40481948852539, 7.03319787979126, 22.766170501708984, 8.9454345703125, 14.400131225585938, 33.372894287109375, 9.339194297790527, 8.902989387512207, 37.21902084350586, 10.373613357543945, 11.015607833862305, 42.66494369506836, 24.49957275390625, 86.2001724243164, 14.610243797302246, 13.992506980895996, 12.38336181640625, 41.282283782958984, 32.45716094970703, 21.91400146484375, 13.24582576751709, 38.098236083984375, 15.921554565429688, 11.951333999633789, 40.52630615234375, 9.151663780212402, 25.72971534729004, 69.66554260253906, 19.97989273071289, 34.30754089355469, 3.999142646789551, 30.77813720703125, 50.32945251464844, 9.891221046447754, 21.990646362304688, 55.45768356323242, 23.37104606628418, 13.863513946533203, 9.439285278320312, 10.59073543548584, 32.333099365234375, 8.926788330078125, 9.048200607299805, 10.753683090209961, 26.2774658203125, 41.363609313964844, 21.30596160888672, 24.651151657104492, 10.931610107421875, 11.40069580078125, 28.845306396484375, 29.893705368041992, 22.269378662109375, 20.921777725219727, 37.01039505004883, 5.877197265625, 7.2259521484375, 19.5096435546875, 14.383336067199707, 23.906494140625, 31.672636032104492, 36.31167221069336, 10.274188995361328, 15.540705680847168, 113.0565185546875, 30.244842529296875, 38.666015625, 24.462324142456055, 11.589072227478027, 65.46305084228516, 24.80135154724121, 50.42068099975586, 43.51008605957031, 31.96308708190918, 9.008577346801758, 28.25067138671875, 15.97430419921875, 9.926528930664062, 31.468597412109375, 25.90876579284668, 16.659820556640625, 42.727874755859375, 12.59893798828125, 22.58259391784668, 22.31488037109375, 5.989766597747803, 11.616164207458496, 10.449615478515625, 35.417938232421875, 11.151615142822266, 24.001922607421875, 51.908538818359375, 43.15277099609375, 29.80380630493164, 9.499740600585938, 23.2752685546875, 9.72067928314209, 13.99542236328125, 96.44046783447266, 63.21242141723633, 10.357177734375, 49.51898193359375, 56.10660171508789, 33.46636962890625, 10.397940635681152, 16.91468620300293, 7.434684753417969, 9.035064697265625, 32.92947006225586, 34.39503479003906, 10.667926788330078, 23.3275146484375, 13.420822143554688, 35.4232177734375, 31.323749542236328, 12.502799987792969, 17.324615478515625, 20.144577026367188, 12.423583984375, 64.46831512451172, 32.17851638793945, 25.30291748046875, 30.622344970703125, 4.749688148498535, 45.71609115600586, 23.52699089050293, 16.242923736572266, 49.21575927734375, 37.14059829711914, 10.048263549804688, 14.743849754333496, 8.12725830078125, 17.387115478515625, 20.25596809387207, 28.84058952331543, 24.187835693359375, 57.867156982421875, 39.53065490722656, 6.083137035369873, 46.85567092895508, 12.604339599609375, 26.90815544128418, 8.3885498046875, 13.815582275390625, 8.07049560546875, 43.72187423706055, 13.91265869140625, 20.126129150390625, 36.693695068359375, 32.0872802734375, 20.351715087890625, 6.8621826171875, 35.10659408569336, 18.815032958984375, 12.452664375305176, 9.268112182617188, 69.97069549560547, 54.51946258544922, 25.495887756347656, 20.48907470703125, 16.66291046142578, 44.07314682006836, 28.73416519165039, 29.460988998413086, 47.49031066894531, 25.21170425415039, 46.24428939819336, 7.003288269042969, 34.1143798828125, 35.35356140136719, 10.95751667022705, 38.47798156738281, 24.696439743041992, 13.902703285217285, 45.56990051269531, 17.90201759338379, 44.14381790161133, 33.87539291381836, 6.5929718017578125, 89.9155044555664, 19.287561416625977, 26.624496459960938, 26.060546875, 21.689254760742188, 29.98552131652832, 13.93877124786377, 6.619165420532227, 15.1475830078125, 46.638031005859375, 36.956787109375, 20.423442840576172, 18.338668823242188, 37.296348571777344, 12.348148345947266, 13.366679191589355, 15.131243705749512, 34.66163635253906, 46.68747329711914, 15.41943359375, 22.090667724609375, 8.667167663574219, 7.990463733673096, 33.65016555786133, 16.3114013671875, 28.460819244384766, 25.763700485229492, 72.64314270019531, 18.649394989013672, 15.53192138671875, 13.306053161621094, 12.242355346679688, 25.737577438354492, 26.71702003479004, 77.38575744628906, 16.114547729492188, 25.70698356628418, 28.43818473815918, 8.859161376953125, 44.21873092651367, 32.56513977050781, 11.034855842590332, 31.46005630493164, 24.87544059753418, 16.47113037109375, 12.31454849243164, 7.7061920166015625, 27.21307373046875, 22.815404891967773, 45.98138427734375, 56.94436264038086, 7.575103759765625, 22.622953414916992, 17.596593856811523, 25.788244247436523, 10.911483764648438, 10.14939022064209, 39.08981704711914, 31.78663444519043, 21.304521560668945, 11.072189331054688, 22.02218246459961, 10.104140281677246, 29.631561279296875, 65.77371215820312, 53.974090576171875, 27.031131744384766, 45.71604537963867, 20.884145736694336, 18.97760009765625, 16.834945678710938, 35.211883544921875, 16.852203369140625, 15.929046630859375, 23.39453125, 44.40212631225586, 20.394943237304688, 23.7802734375, 13.959599494934082, 7.5867462158203125, 24.91507339477539, 23.44482421875, 32.83851623535156, 32.92730712890625, 2.5763320922851562, 20.180282592773438, 18.650070190429688, 26.42747688293457, 21.68194580078125, 9.743484497070312, 17.767181396484375, 37.75498962402344, 1.79497492313385, 2.4635655879974365, 1.4146791696548462, 2.4673755168914795, 0.9188833236694336, 1.4910231828689575, 1.8637956380844116, 1.455407738685608, 1.3235138654708862, 1.6883447170257568, 3.074913263320923, 9.5367431640625e-07, 1.4999974966049194, 1.4578945636749268, 2.427220344543457, 2.0453991889953613, 1.6275200843811035, 2.3276028633117676, 2.0518367290496826, 2.1879141330718994, 1.740355372428894, 0.900585412979126, 3.0055313110351562, 2.025200843811035, 1.8689430952072144, 2.6199371814727783, 2.5337436199188232, 1.9084619283676147, 0.8423241972923279, 0.8222341537475586, 1.9176671504974365, 2.34084415435791, 1.4120131731033325, 2.3359289169311523, 2.4045419692993164, 1.3213244676589966, 3.0220348834991455, 2.721921920776367, 1.6315386295318604, 1.5481815338134766, 1.876516342163086, 2.2620880603790283, 1.6315826177597046, 1.2742643356323242, 1.329085350036621, 0.8641471862792969, 1.733500599861145, 1.1157540082931519, 0.9508143663406372, 2.0443124771118164, 2.094906806945801, 2.357041358947754, 2.078719139099121, 1.7077172994613647, 2.3460845947265625, 1.3814277648925781, 1.256325602531433, 2.074070930480957, 0.4166158139705658, 2.2256689071655273, 1.3142385482788086, 1.4555822610855103, 2.399756908416748, 2.3562393188476562, 2.792459726333618, 1.167220115661621, 1.44035005569458, 1.4782227277755737, 1.7231550216674805, 1.282297968864441, 2.438298225402832, 1.3434019088745117, 2.0403709411621094, 2.2643511295318604, 1.5023113489151, 2.027832508087158, 2.174276113510132, 9.5367431640625e-07, 1.5248595476150513, 1.7358880043029785, 1.4378951787948608, 1.8037127256393433, 2.188163995742798, 1.5794423818588257, 0.7440834045410156, 2.0256757736206055, 2.38934588432312, 3.108858823776245, 2.409031629562378, 2.3290672302246094, 1.2402067184448242, 1.9674023389816284, 0.031294822692871094, 1.6777759790420532, 2.074538230895996, 2.41526460647583, 1.416170358657837, 1.6911239624023438, 1.8858678340911865, 1.990375280380249, 1.6489816904067993, 2.6611664295196533, 1.9627408981323242, 1.0382989645004272, 1.8168457746505737, 1.8715676069259644, 1.396748423576355, 2.214120864868164, 1.8970612287521362, 1.4397858381271362, 2.071049690246582, 1.6584786176681519, 3.103363513946533, 2.5716490745544434, 2.5275683403015137, 1.769307017326355, 2.4387691020965576, 2.0062646865844727, 1.9088549613952637, 1.8048908710479736, 1.3521952629089355, 2.1898622512817383, 2.145195722579956, 2.021740674972534, 1.7773863077163696, 2.4567699432373047, 1.2322149276733398, 1.3413420915603638, 1.5334861278533936, 1.8170499801635742, 1.2670328617095947, 2.944636106491089, 1.5251537561416626, 1.2036947011947632, 9.5367431640625e-07, 1.8221038579940796, 2.3001022338867188, 2.793194532394409, 1.5712848901748657, 1.8696731328964233, 2.1786770820617676, 2.9370036125183105, 2.7006866931915283, 1.475825309753418, 1.337183952331543, 1.426375389099121, 2.5904948711395264, 1.1359598636627197, 2.508049964904785, 2.606508731842041, 1.8308724164962769, 1.6887502670288086, 2.902022123336792, 9.5367431640625e-07, 1.295644760131836, 2.446666717529297, 1.4966506958007812, 2.9587810039520264, 1.303568959236145, 1.6706053018569946, 2.284703254699707, 2.4224276542663574, 1.2884511947631836, 2.6106021404266357, 1.5559266805648804, 1.6831035614013672, 1.1680707931518555, 1.6249849796295166, 1.8027234077453613, 1.5467950105667114, 1.6400521993637085, 2.2957115173339844, 1.3678829669952393, 1.1507121324539185, 1.3458999395370483, 1.9856046438217163, 1.5749043226242065, 2.9273273944854736, 1.1711798906326294, 3.1007323265075684, 2.2609214782714844, 1.5486016273498535, 0.889399528503418, 1.4647685289382935, 2.860013723373413, 1.1875962018966675, 1.2566099166870117, 2.1770474910736084, 1.342185139656067, 2.5671892166137695, 1.4427906274795532, 1.571623682975769, 2.9118378162384033, 1.0479003190994263, 0.9186887741088867, 1.7066198587417603, 1.1961402893066406, 2.003234386444092, 2.071808338165283, 1.9475202560424805, 0.6363592147827148, 2.1277389526367188, 3.0642082691192627, 2.1889660358428955, 1.7261148691177368, 2.24826717376709, 1.3518450260162354, 1.3127622604370117, 1.5251874923706055, 1.9066818952560425, 2.0000152587890625, 1.2560653686523438, 1.0272588729858398, 1.4786226749420166, 2.2248079776763916, 1.1789963245391846, 1.9070769548416138, 2.7038605213165283, 2.3241286277770996, 1.835768699645996, 1.5989197492599487, 1.129134178161621, 2.012763023376465, 1.7173696756362915, 1.6314743757247925, 2.7658419609069824, 1.8254324197769165, 2.2429068088531494, 1.2607468366622925, 3.696617841720581, 1.7400561571121216, 1.4808374643325806, 2.061476945877075, 1.6462174654006958, 2.8616344928741455, 1.6593445539474487, 1.5818756818771362, 1.5327837467193604, 2.1001482009887695, 2.5888171195983887, 1.5803238153457642, 1.3387417793273926, 1.9033211469650269, 0.7070198059082031, 2.3868637084960938, 1.0063608884811401, 2.307939291000366, 2.1183419227600098, 1.5787171125411987, 1.648520827293396, 1.8384100198745728, 1.4723159074783325, 2.4162988662719727, 1.8321642875671387, 1.5806913375854492, 2.465639352798462, 0.9768829345703125, 2.3097996711730957, 0.9126541018486023, 1.6057157516479492, 1.9204403162002563, 2.991218090057373, 2.401209592819214, 2.2327260971069336, 2.0247373580932617, 2.7050247192382812, 1.107478141784668, 2.034064292907715, 1.3175976276397705, 2.042487621307373, 2.0113391876220703, 1.0857627391815186, 1.82905113697052, 2.923616886138916, 1.1303786039352417, 1.8265656232833862, 0.711941659450531, 2.3192496299743652, 1.5481595993041992, 1.4686307907104492, 1.4843368530273438, 1.421339988708496, 1.5556135177612305, 2.0031063556671143, 2.118670701980591, 1.6957333087921143, 1.3146179914474487, 1.9079445600509644, 2.0251073837280273, 1.437516450881958, 1.4745186567306519, 1.6824986934661865, 1.7217663526535034, 1.2275829315185547, 3.0341484546661377, 1.7693734169006348, 3.431899309158325, 1.2632017135620117, 2.2358007431030273, 1.58269202709198, 0.025974269956350327, 0.05601942911744118, 0.03936436027288437, 0.0725322961807251, 0.05459308624267578, 0.04752185568213463, 0.07591133564710617, 0.006899719592183828, 0.0007251054048538208, 0.044741399586200714, 0.03401242569088936, 0.005090188235044479, 0.0008938515093177557, 0.0488886833190918, 0.03717350959777832, 0.01243627443909645, 0.05558306723833084, 0.053463101387023926, 0.06691497564315796, 0.08573222160339355, 0.0012863498413935304, 0.06132901832461357, 0.07231771945953369, 0.029542211443185806, 0.042206790298223495, 0.0849146842956543, 0.008969255723059177, 0.05701084062457085, 0.006669992581009865, 0.050083935260772705, 0.06528667360544205, 0.04529093578457832, 0.035752177238464355, 0.0395805761218071, 0.040583379566669464, 0.09613507986068726, 0.11511588841676712, 0.09009766578674316, 0.014768823981285095, 0.13153603672981262, 0.0, 0.10424233973026276, 0.025174569338560104, 0.09138040244579315, 0.07781237363815308, 0.07045958191156387, 0.02645057439804077, 6.178855983307585e-05, 0.06051595136523247, 0.02154676429927349, 0.030064523220062256, 0.05396277830004692, 0.031489863991737366, 0.12042199820280075, 0.039614055305719376, 0.03097253292798996, 0.0826709121465683, 0.04633438587188721, 0.06345120817422867, 0.03351491689682007, 0.016634484753012657, 0.05530412495136261, 0.03575563430786133, 0.03575742244720459, 0.030511682853102684, 0.011565892025828362, 0.022226329892873764, 0.03886367753148079, 0.003576824674382806, 0.08745449781417847, 0.04798377305269241, 0.005656696390360594, 0.018889103084802628, 0.004980207420885563, 0.0815577283501625, 0.05598468706011772, 0.03578072786331177, 0.08951859921216965, 0.0619671605527401, 0.11669664829969406, 0.07267990708351135, 0.06634856015443802, 0.008653387427330017, 0.0030096727423369884, 0.06780409812927246, 0.08629045635461807, 0.029691051691770554, 0.024512887001037598, 0.03341735154390335, 0.03937385231256485, 0.012180333025753498, 0.030712302774190903, 0.10239718854427338, 0.06922566145658493, 0.05369668826460838, 0.04464242234826088, 0.032431550323963165, 0.06075620651245117, 0.0767049789428711, 0.013645014725625515, 0.02974707819521427, 0.006540840025991201, 0.09541530162096024, 0.009636645205318928, 0.05407136678695679, 0.03355517238378525, 0.047603391110897064, 0.0354389026761055, 0.09645861387252808, 0.08839758485555649, 0.05934858322143555, 0.0454179048538208, 0.001426104223355651, 0.09345420449972153, 0.008152604103088379, 0.09189706295728683, 0.00611847685649991, 0.02420523576438427, 0.09593208879232407, 0.07051295042037964, 0.018358631059527397, 0.08258276432752609, 0.03060736320912838, 0.044490884989500046, 0.03631186485290527, 0.03346122056245804, 0.08263026177883148, 0.07037156075239182, 0.06598609685897827, 0.07687914371490479, 0.063914954662323, 0.06876832991838455, 0.02789938636124134, 0.004681283142417669, 0.014460992068052292, 0.0012767905136570334, 0.0362490676343441, 0.028036832809448242, 0.062059640884399414, 0.07064057886600494, 0.020983338356018066, 0.038035277277231216, 0.05280506610870361, 0.0, 0.05817151069641113, 0.03136470541357994, 0.035978782922029495, 3.126919182250276e-05, 0.039546411484479904, 0.10082607716321945, 0.05462849140167236, 0.04033644497394562, 0.01150718703866005, 0.022320929914712906, 0.0391044095158577, 0.047498393803834915, 0.014189214445650578, 0.004432561807334423, 0.06739220768213272, 0.07192362844944, 0.06914860755205154, 0.027752451598644257, 0.051357563585042953, 0.03221970796585083, 0.040307577699422836, 0.06570188701152802, 0.0014943855348974466, 0.01291109248995781, 0.06868171691894531, 0.05087989568710327, 0.06134403869509697, 0.05466071143746376, 0.06592468172311783, 1.1932850156881614e-06, 0.11775803565979004, 0.03555708006024361, 0.021275438368320465, 0.07525944709777832, 0.041628122329711914, 0.04481804370880127, 0.07806006819009781, 0.13244207203388214, 0.05303187295794487, 0.04053139686584473, 0.00451350212097168, 0.03495532274246216, 0.05299532786011696, 0.08371000736951828, 0.07552094012498856, 0.003261150559410453, 0.07861912250518799, 0.002684700535610318, 0.0742601752281189, 0.04766891896724701, 0.02423158846795559, 0.02789938449859619, 0.08767908066511154, 0.018908143043518066, 0.09451819956302643, 0.016363749280571938, 0.053882718086242676, 0.1309501975774765, 0.0516541562974453, 0.04009287804365158, 0.05042630061507225, 0.02311713807284832, 0.08442419767379761, 0.0974145233631134, 0.1109355017542839, 0.07251401990652084, 0.08099416643381119, 0.03379372879862785, 0.029864629730582237, 0.05898064374923706, 0.02645057439804077, 0.0180930495262146, 0.0561518669128418, 0.004884053487330675, 0.031782105565071106, 0.10629331320524216, 0.029517829418182373, 0.06377431005239487, 0.03623742237687111, 0.08708759397268295, 0.11886655539274216, 0.03495188429951668, 0.04022988677024841, 0.04262761399149895, 0.0295331422239542, 0.02754843235015869, 0.09146963804960251, 0.06030578166246414, 0.05829842388629913, 0.05278092622756958, 0.15495149791240692, 0.013428179547190666, 0.04692445695400238, 0.027133285999298096, 0.012516438961029053, 0.022507857531309128, 0.015053869225084782, 0.12856841087341309, 0.05988295376300812, 0.03034069761633873, 0.020548909902572632, 0.057965993881225586, 0.02150578238070011, 0.08041959255933762, 0.04169881343841553, 0.09900914877653122, 0.08115478605031967, 0.0021674686577171087, 0.05220285430550575, 0.06423097103834152, 0.02954033389687538, 0.021191291511058807, 0.015596449375152588, 0.06045812368392944, 0.06370562314987183, 0.03590250015258789, 0.09626287966966629, 0.08231746405363083, 0.10031036287546158, 0.05182027816772461, 0.02575528994202614, 0.0, 0.08757976442575455, 0.028739511966705322, 0.00937462504953146, 0.00259137200191617, 0.005867904983460903, 0.034948647022247314, 0.027909401804208755, 0.03713551536202431, 0.07322680950164795, 0.05802074447274208, 0.053025975823402405, 0.03933781385421753, 0.041628122329711914, 0.041316837072372437, 0.07593517750501633, 0.10637801885604858, 0.03343890979886055, 0.049647148698568344, 0.10249916464090347, 0.0515102855861187, 0.058325570076704025, 0.07402122765779495, 0.1435527801513672, 0.021865462884306908, 0.11172771453857422, 0.01791203022003174, 0.11329454183578491, 0.0009180289343930781, 0.09712989628314972, 0.040417637676000595, 0.04045775160193443, 0.044470109045505524, 0.044559020549058914, 0.04813309386372566, 0.37419435381889343, 0.4765918254852295, 0.6266875863075256, 0.4447101354598999, 0.29155054688453674, 0.29150256514549255, 0.3417767584323883, 0.09011391550302505, 0.26183316111564636, 0.21206815540790558, 0.5693765878677368, 0.6015489101409912, 0.3410370647907257, 0.35354137420654297, 0.11549756675958633, 0.6105929017066956, 0.5858888030052185, 0.4819895327091217, 0.39857131242752075, 4.024120971748936e-15, 0.2485535591840744, 0.5104812383651733, 0.40732017159461975, 0.19170808792114258, 0.5748240351676941, 0.22102542221546173, 0.13353325426578522, 0.3529907166957855, 0.18112130463123322, 0.09880410879850388, 0.327860951423645, 0.19814369082450867, 0.5948318243026733, 0.29221704602241516, 0.26854053139686584, 0.24336464703083038, 0.26283931732177734, 0.2671254873275757, 0.36619582772254944, 0.21955370903015137, 0.14225786924362183, 0.2979392111301422, 0.21186824142932892, 0.40523016452789307, 0.22646880149841309, 0.20726600289344788, 0.47976431250572205, 0.5555076599121094, 0.15407535433769226, 0.3305070102214813, 0.30822622776031494, 0.22680436074733734, 0.21459229290485382, 0.2277267426252365, 0.5945699214935303, 0.30846890807151794, 0.5174174904823303, 0.6051311492919922, 0.648127555847168, 0.41792598366737366, 0.11868610233068466, 0.20376773178577423, 0.10131452232599258, 0.5320311784744263, 0.029409008100628853, 0.5949302315711975, 0.291564404964447, 0.502086341381073, 0.4533430337905884, 0.47473371028900146, 0.29600897431373596, 0.09733300656080246, 0.21637248992919922, 0.40545177459716797, 0.4841082692146301, 0.3283900320529938, 0.24998797476291656, 0.6408525705337524, 0.2064349353313446, 0.31010788679122925, 0.4082038402557373, 0.324175089597702, 0.3719697594642639, 0.43277204036712646, 0.4136209785938263, 0.5468566417694092, 0.3184601664543152, 0.17242637276649475, 0.11679361015558243, 0.28438520431518555, 0.42704764008522034, 0.2694398760795593, 0.22115929424762726, 0.6152116060256958, 0.46176496148109436, 0.19303488731384277, 0.0877026915550232, 0.5688820481300354, 0.2811352610588074, 0.4729640483856201, 0.2314314842224121, 0.5245961546897888, 0.354378342628479, 0.3711681365966797, 0.1306060254573822, 0.15065346658229828, 0.12423157691955566, 0.11446323245763779, 0.3443036675453186, 0.26731637120246887, 0.6722558736801147, 0.2319916933774948, 0.17108021676540375, 0.5248389840126038, 0.3936857581138611, 0.4344388544559479, 0.08504094928503036, 0.47127246856689453, 4.791825471844608e-15, 0.167447030544281, 0.3178010582923889, 0.360333114862442, 0.237306609749794, 0.5856784582138062, 0.3333279490470886, 0.108448825776577, 0.20753557980060577, 0.32142168283462524, 0.2529515027999878, 0.1324499398469925, 0.16737280786037445, 0.3349066376686096, 0.5960601568222046, 0.31653252243995667, 0.2995567321777344, 0.2763880789279938, 0.20254428684711456, 0.26713961362838745, 0.4672003388404846, 0.24433620274066925, 0.44302886724472046, 0.4059801399707794, 0.08117315173149109, 0.1608625054359436, 0.2814423143863678, 0.2149595469236374, 0.33781853318214417, 0.277581125497818, 0.4015105366706848, 0.19304116070270538, 0.679167628288269, 0.4292459487915039, 0.22634446620941162, 0.26961344480514526, 0.4366845190525055, 0.29634177684783936, 0.2413221150636673, 0.4180682897567749, 0.33481544256210327, 0.3406652808189392, 0.39474138617515564, 0.2506997287273407, 0.32337233424186707, 0.2822920083999634, 0.4001966118812561, 0.003848077030852437, 0.3979150950908661, 0.43202170729637146, 0.46286535263061523, 0.20647014677524567, 0.1718568354845047, 0.5138639807701111, 0.16974838078022003, 0.11413444578647614, 0.5282189846038818, 0.31325793266296387, 0.2971835136413574, 0.272388756275177, 0.22840876877307892, 0.35745540261268616, 0.41772809624671936, 0.15436509251594543, 0.5791112184524536, 0.41519472002983093, 0.16954810917377472, 0.1475372016429901, 0.115175262093544, 0.2702583968639374, 0.3553929924964905, 0.5933908224105835, 0.16731151938438416, 0.3134685158729553, 0.2375890612602234, 0.2832484245300293, 0.30850037932395935, 0.4934251308441162, 0.08593118190765381, 0.21761539578437805, 0.17627234756946564, 0.48772528767585754, 0.4383775293827057, 0.4115874469280243, 0.33439159393310547, 0.4661182165145874, 0.2986466586589813, 0.30536699295043945, 0.24376721680164337, 0.6334785223007202, 0.3258616328239441, 0.5674229264259338, 0.10398972034454346, 0.47165626287460327, 0.5863229036331177, 0.274671733379364, 0.3449050188064575, 0.28126609325408936, 0.5361520051956177, 0.4290987253189087, 0.3220742642879486, 0.5407712459564209, 0.2753269374370575, 0.16405773162841797, 0.4482067823410034, 0.16045433282852173, 0.6814877390861511, 0.37183958292007446, 0.43836578726768494, 0.1818409264087677, 0.25207117199897766, 0.25964248180389404, 0.2615279257297516, 0.33584895730018616, 0.5649513602256775, 0.19054365158081055, 0.4199635088443756, 0.10210487246513367, 0.37051719427108765, 0.359652578830719, 0.0872177854180336, 0.4665911793708801, 0.22784990072250366, 0.16484566032886505, 0.08486499637365341, 0.23467694222927094, 0.19504085183143616, 0.5459370613098145, 0.31370851397514343, 0.11912300437688828, 0.32990461587905884, 0.17866666615009308, 0.4170181453227997, 0.34820064902305603, 0.2777899205684662, 0.15630875527858734, 0.3555540442466736, 0.3615039885044098, 0.37236037850379944, 0.4132266938686371, 0.7869476079940796, 0.09551652520895004, 0.4452565312385559, 0.3227696120738983, 0.6917018890380859, 0.2328290194272995, 0.6784795522689819, 0.29630181193351746, 0.2940064072608948, 0.2718988060951233, 0.358661413192749, 0.16937020421028137, 0.42515844106674194, 0.3815036714076996, 0.36071503162384033, 0.14146442711353302, 0.3484121561050415, 0.4608127176761627, 0.6869984865188599, 0.17161186039447784, 0.3491610586643219, 0.36319929361343384, 0.5161184072494507, 0.31400996446609497, 0.320356547832489, 0.37609782814979553, 0.09728492796421051, 0.31453314423561096, 0.6876075863838196, 0.18133346736431122, 0.34396225214004517, 0.35662031173706055, 0.46208426356315613, 0.0887465849518776, 0.4481847286224365, 0.1085166335105896, 0.22325442731380463, 0.6749016642570496, 0.18332484364509583, 0.23519288003444672, 0.3208736479282379, 0.17353244125843048, 15.7960786819458, 28.410934448242188, 31.657968521118164, 17.308860778808594, 25.816070556640625, 11.342002868652344, 26.085556030273438, 9.011253356933594, 19.93531036376953, 27.012922286987305, 9.704833984375, 31.380172729492188, 12.73541259765625, 10.467177391052246, 14.224809646606445, 16.99371337890625, 22.70551872253418, 45.47168731689453, 24.89204216003418, 10.460983276367188, 18.549774169921875, 13.06501579284668, 30.1732177734375, 11.055877685546875, 21.061264038085938, 21.07061004638672, 8.556965827941895, 14.384368896484375, 20.07819938659668, 17.31075096130371, 11.059706687927246, 14.981708526611328, 25.296300888061523, 19.88201904296875, 14.3951997756958, 14.104354858398438, 36.34327697753906, 22.833112716674805, 16.330827713012695, 9.03913402557373, 50.013465881347656, 17.668548583984375, 10.343048095703125, 10.23038387298584, 41.87622833251953, 19.9810791015625, 16.0941162109375, 17.363388061523438, 14.806503295898438, 75.7921142578125, 18.977020263671875, 29.50287437438965, 15.400458335876465, 7.029045104980469, 8.053863525390625, 31.952072143554688, 25.50758171081543, 11.767684936523438, 29.462753295898438, 35.771766662597656, 18.860626220703125, 50.18886947631836, 10.83053970336914, 23.706083297729492, 18.499847412109375, 22.411298751831055, 19.98463249206543, 12.69708251953125, 13.7977294921875, 19.26617431640625, 11.251373291015625, 32.665863037109375, 22.594085693359375, 11.285568237304688, 25.290555953979492, 32.52403259277344, 7.000274658203125, 35.767303466796875, 40.04779052734375, 41.618568420410156, 81.22186279296875, 33.279083251953125, 42.57162857055664, 8.58984375, 41.40998840332031, 18.100341796875, 30.241552352905273, 10.173419952392578, 14.00677490234375, 31.44416618347168, 12.880202293395996, 16.80259895324707, 17.05482292175293, 24.77027702331543, 39.92234420776367, 12.215353965759277, 20.683427810668945, 29.095462799072266, 29.641584396362305, 9.98876953125, 33.17294692993164, 13.683676719665527, 17.95672607421875, 8.043968200683594, 13.342348098754883, 19.993953704833984, 11.989066123962402, 12.096010208129883, 18.506202697753906, 31.456937789916992, 8.983551025390625, 46.37535095214844, 11.667677879333496, 33.21467590332031, 30.058061599731445, 10.090957641601562, 15.295759201049805, 24.810699462890625, 15.011260986328125, 15.017370223999023, 5.7874908447265625, 51.91079330444336, 29.647750854492188, 8.360909461975098, 39.611175537109375, 63.16120910644531, 31.624557495117188, 26.67755126953125, 13.776622772216797, 32.87771987915039, 8.20257568359375, 16.282501220703125, 51.84954071044922, 11.898197174072266, 12.739006042480469, 81.31330871582031, 39.04353332519531, 43.10434341430664, 29.1142635345459, 10.1240234375, 6.694549560546875, 11.268783569335938, 15.249298095703125, 31.025747299194336, 37.40934371948242, 12.743331909179688, 11.27496337890625, 34.04170227050781, 17.317298889160156, 25.98481559753418, 23.17078971862793, 15.457427978515625, 47.45290756225586, 39.69358825683594, 45.27235412597656, 11.818304061889648, 27.373870849609375, 11.494613647460938, 20.060611724853516, 9.078475952148438, 24.4783935546875, 15.715624809265137, 67.56621551513672, 74.02840423583984, 26.665740966796875, 16.07659912109375, 19.23223114013672, 8.127548217773438, 27.372127532958984, 17.767333984375, 11.766769409179688, 10.463790893554688, 6.531104564666748, 20.069068908691406, 52.52650451660156, 18.99151039123535, 26.61702537536621, 22.207870483398438, 14.160125732421875, 16.884078979492188, 90.79610443115234, 23.80915641784668, 15.1578369140625, 13.717543601989746, 42.704803466796875, 10.25654125213623, 11.108983993530273, 35.63157653808594, 60.60032272338867, 16.54847526550293, 21.488815307617188, 53.49546813964844, 25.214345932006836, 8.022906303405762, 14.141974449157715, 20.957059860229492, 16.83997917175293, 21.83708381652832, 23.705795288085938, 13.747161865234375, 68.91242980957031, 12.157623291015625, 27.3350772857666, 20.191436767578125, 10.715468406677246, 11.811925888061523, 31.67298698425293, 40.81317138671875, 27.953048706054688, 17.29258918762207, 28.98681640625, 27.022384643554688, 22.57118034362793, 22.439462661743164, 15.424530029296875, 21.567794799804688, 21.320892333984375, 36.40534210205078, 19.71820831298828, 48.80084991455078, 51.08234405517578, 14.925994873046875, 26.135116577148438, 12.190109252929688, 37.486053466796875, 27.882293701171875, 30.24631118774414, 25.801542282104492, 8.3419189453125, 25.37813377380371, 17.79710578918457, 23.69708251953125, 24.51424217224121, 26.756072998046875, 21.09771728515625, 17.055389404296875, 17.636524200439453, 11.75628662109375, 36.48466873168945, 30.696456909179688, 13.34261417388916, 15.80059814453125, 10.416718482971191, 26.18603515625, 17.308095932006836, 31.786590576171875, 23.10112953186035, 38.23788833618164, 59.50149154663086, 25.989402770996094, 18.805938720703125, 30.412084579467773, 12.495697021484375, 9.22021484375, 13.842025756835938, 12.710617065429688, 16.820207595825195, 28.57794189453125, 14.913283348083496, 8.994786262512207, 29.73817253112793, 10.797378540039062, 17.985435485839844, 21.167753219604492, 10.419464111328125, 36.02762985229492, 11.623260498046875, 11.881126403808594, 20.000961303710938, 59.2232780456543, 21.741432189941406, 11.488571166992188, 10.454742431640625, 32.35833740234375, 8.777587890625, 20.527982711791992, 9.053009033203125, 36.745361328125, 12.017730712890625, 46.4326171875, 53.58567428588867, 36.81195068359375, 31.363187789916992, 7.076708793640137, 43.684120178222656, 31.445419311523438, 9.82425594329834, 18.51692771911621, 6.1911468505859375, 35.02962875366211, 11.749176025390625, 8.937881469726562, 12.530792236328125, 8.645309448242188, 12.811415672302246, 9.292841911315918, 27.9754581451416, 11.1177978515625, 12.013165473937988, 40.389549255371094, 1.7074565887451172, 1.3759914636611938, 1.2121992111206055, 1.3712148666381836, 1.6129255294799805, 1.5196541547775269, 1.6505815982818604, 1.6545569896697998, 2.0384435653686523, 1.1530332565307617, 1.5419563055038452, 1.83014976978302, 2.0085394382476807, 1.8430527448654175, 1.9183014631271362, 1.626766324043274, 2.3059749603271484, 1.2283943891525269, 2.2498598098754883, 2.1281309127807617, 1.7851074934005737, 1.967979073524475, 2.7031190395355225, 2.6708126068115234, 1.7302111387252808, 1.45927894115448, 0.9219712615013123, 1.8561495542526245, 0.6003122329711914, 1.4433012008666992, 2.571244478225708, 1.5702046155929565, 1.2261152267456055, 1.624173641204834, 2.217637062072754, 2.2139434814453125, 1.892985463142395, 2.006817102432251, 1.876961588859558, 2.6893413066864014, 2.6550683975219727, 2.7009670734405518, 2.9049389362335205, 2.0637800693511963, 0.8649082183837891, 2.1889729499816895, 2.15303897857666, 1.4858465194702148, 1.104103922843933, 1.9768657684326172, 2.2626712322235107, 1.9069753885269165, 2.256585121154785, 2.6210949420928955, 1.6022578477859497, 1.9712998867034912, 1.948411464691162, 2.008483409881592, 2.1535868644714355, 1.9069069623947144, 2.673853635787964, 3.0297601222991943, 2.036817789077759, 3.630711555480957, 2.9285120964050293, 1.6337080001831055, 2.331692695617676, 1.5472382307052612, 1.8676499128341675, 2.725182056427002, 1.5204590559005737, 1.542548656463623, 1.8483915328979492, 2.078765630722046, 1.8226864337921143, 3.2757949829101562, 2.223308563232422, 1.6138757467269897, 2.416905403137207, 1.2904226779937744, 1.3858290910720825, 1.4519394636154175, 1.6160564422607422, 2.257607936859131, 1.8666458129882812, 3.1160266399383545, 1.729622483253479, 1.9158135652542114, 1.2237567901611328, 1.6357125043869019, 1.7835091352462769, 2.176567316055298, 1.9394636154174805, 1.564900517463684, 2.4200596809387207, 1.2493460178375244, 1.8887243270874023, 0.6085999011993408, 1.1311941146850586, 1.289833903312683, 1.5300568342208862, 1.86351478099823, 1.3644475936889648, 1.698927879333496, 2.403949737548828, 1.6693328619003296, 1.5224462747573853, 3.4636735916137695, 2.491605281829834, 1.464692234992981, 2.0892693996429443, 1.8998812437057495, 1.3012380599975586, 1.4522980451583862, 2.5508222579956055, 1.7405747175216675, 1.4237433671951294, 2.024120330810547, 1.5605653524398804, 2.131838083267212, 2.0128896236419678, 1.5311976671218872, 2.6298668384552, 1.187918782234192, 0.8274478912353516, 1.5693939924240112, 2.3479063510894775, 1.9554799795150757, 3.154620409011841, 1.4155679941177368, 1.9823150634765625, 2.830235242843628, 2.37606143951416, 1.9750031232833862, 1.8782645463943481, 1.054726481437683, 1.3629920482635498, 2.089613199234009, 1.7752878665924072, 0.6854429244995117, 2.9370336532592773, 1.2091054916381836, 2.4115524291992188, 1.2958840131759644, 2.0303046703338623, 1.9809870719909668, 1.578028678894043, 1.0681638717651367, 0.6557149887084961, 1.8026913404464722, 1.0456093549728394, 2.64083194732666, 2.4917819499969482, 1.0153602361679077, 1.752732515335083, 1.783784031867981, 2.0643811225891113, 1.2866170406341553, 1.2286139726638794, 2.6077792644500732, 2.246835470199585, 2.1620540618896484, 1.927615761756897, 2.204390525817871, 1.6591547727584839, 2.0349669456481934, 1.8324346542358398, 1.5209379196166992, 1.6362218856811523, 1.4509705305099487, 2.272891044616699, 2.0055437088012695, 0.9647970199584961, 1.2437505722045898, 1.9023089408874512, 1.9148627519607544, 1.7978096008300781, 1.374897837638855, 1.584303855895996, 1.3824071884155273, 2.0204553604125977, 2.706038236618042, 1.2442928552627563, 2.3360376358032227, 2.4139370918273926, 2.414393901824951, 1.0365723371505737, 2.539844274520874, 3.3964686393737793, 1.1934548616409302, 1.5278006792068481, 1.813577651977539, 1.8306450843811035, 2.4435665607452393, 1.8006582260131836, 1.3485482931137085, 2.7732226848602295, 2.1279797554016113, 2.050124168395996, 1.770066738128662, 2.402646064758301, 2.832995653152466, 1.450892448425293, 1.8986740112304688, 1.2863759994506836, 1.5716387033462524, 1.4497835636138916, 2.2164783477783203, 2.5139036178588867, 0.09972868114709854, 2.0088605880737305, 3.105792760848999, 2.703674793243408, 1.872744083404541, 2.66137957572937, 1.0846889019012451, 1.290377140045166, 1.7479981184005737, 0.901852548122406, 1.4171117544174194, 1.870736002922058, 2.8896727561950684, 0.7996105551719666, 2.5277135372161865, 1.8930892944335938, 2.7752766609191895, 0.5175333023071289, 2.5997722148895264, 2.194836378097534, 2.2654104232788086, 1.7675317525863647, 1.522312879562378, 1.327229380607605, 1.446131706237793, 2.3725714683532715, 2.1171622276306152, 0.9702576994895935, 2.5923707485198975, 2.183387517929077, 2.281291961669922, 1.2685766220092773, 2.086073875427246, 1.8521093130111694, 2.0971713066101074, 2.019970655441284, 1.4015172719955444, 1.778102993965149, 1.80174720287323, 1.8265312910079956, 3.1322221755981445, 2.894268751144409, 2.235130548477173, 1.768370509147644, 1.3960342407226562, 2.232802152633667, 1.4841467142105103, 1.3824471235275269, 2.362934112548828, 1.3996047973632812, 1.2454519271850586, 1.8822563886642456, 1.1019916534423828, 2.954517126083374, 1.7957355976104736, 2.482619524002075, 1.6011513471603394, 1.5713170766830444, 1.7062673568725586, 1.5155630111694336, 1.468214988708496, 1.796212077140808, 1.9671354293823242, 2.2854795455932617, 1.7944121360778809, 1.7323637008666992, 1.2661504745483398, 2.401643991470337, 2.470889091491699, 1.950308918952942, 1.3756879568099976, 1.0249894857406616, 1.4140958786010742, 1.9592161178588867, 0.7838811874389648, 2.498359441757202, 2.365246057510376, 1.2662628889083862, 2.015977382659912, 2.176590919494629, 1.3949308395385742, 1.8338934183120728, 1.626143455505371, 2.1827516555786133, 1.1657934188842773, 1.7313140630722046, 1.3931636810302734, 1.8210668563842773, 1.6113920211791992, 1.5672903060913086, 1.0211868286132812, 0.06790949404239655, 0.003591905115172267, 0.08064049482345581, 0.06381756067276001, 0.01751408539712429, 0.049600958824157715, 0.13222259283065796, 0.03441731259226799, 0.02424495667219162, 0.05883515626192093, 0.0724448710680008, 0.0386459156870842, 0.01863032579421997, 0.06645703315734863, 0.02088911086320877, 0.026365656405687332, 0.032016169279813766, 0.02318716049194336, 0.020989537239074707, 0.07717359811067581, 0.02161707915365696, 0.06631821393966675, 0.0498347282409668, 0.07877892255783081, 0.025458678603172302, 0.06974980235099792, 0.061522386968135834, 0.02327839285135269, 0.05094432830810547, 0.047243185341358185, 0.0760648176074028, 0.0606512613594532, 0.05763991177082062, 0.020710166543722153, 0.025384128093719482, 0.05879981815814972, 0.14408445358276367, 0.05243369936943054, 0.0651131346821785, 0.06623583287000656, 0.040706660598516464, 0.03221025690436363, 0.012528185732662678, 0.037324219942092896, 0.007264086976647377, 0.014316282235085964, 0.0881405919790268, 0.0065933470614254475, 0.059602826833724976, 0.007564229425042868, 0.05697565898299217, 0.06921947002410889, 0.021695973351597786, 0.12568527460098267, 0.06779227405786514, 0.05286620929837227, 0.08552287518978119, 0.045361220836639404, 0.04694144055247307, 0.049458060413599014, 0.10756953805685043, 0.10175759345293045, 0.017572598531842232, 0.030027274042367935, 0.040614545345306396, 0.03176148235797882, 0.02612927556037903, 0.02953297086060047, 0.08639261871576309, 0.06576541066169739, 0.07856392860412598, 0.048970699310302734, 0.12220656871795654, 0.00010838746675290167, 0.09499025344848633, 0.03724934160709381, 0.0055204033851623535, 0.10284069925546646, 0.06745292246341705, 0.03314575180411339, 0.05094432830810547, 0.04915602505207062, 0.07413572072982788, 0.07645668089389801, 0.0441863089799881, 0.021054791286587715, 0.000631863484159112, 0.1026369258761406, 0.054440394043922424, 0.04371512681245804, 0.09609678387641907, 0.05399027839303017, 0.1050170287489891, 0.11728447675704956, 0.060025010257959366, 0.05007747933268547, 0.0, 0.18498456478118896, 0.002013447927311063, 0.04410775378346443, 0.07985277473926544, 0.15441036224365234, 0.03352758660912514, 0.06723251193761826, 0.06618613749742508, 0.03255913034081459, 0.0962333083152771, 0.04470985382795334, 0.027662018314003944, 0.008113741874694824, 0.053818464279174805, 0.12836506962776184, 0.02789938449859619, 0.06174527853727341, 0.050462882965803146, 0.10920026898384094, 0.06675984710454941, 0.09241795539855957, 0.0, 0.04783431068062782, 0.06260877102613449, 0.010426359251141548, 0.005909919738769531, 0.08332502096891403, 0.06478314846754074, 0.05796404555439949, 0.069073885679245, 0.03713257610797882, 0.0010415189899504185, 0.0633171796798706, 0.03775686025619507, 0.046238936483860016, 0.06999149173498154, 0.03982722759246826, 0.045143213123083115, 0.09569308161735535, 0.06512561440467834, 0.0481640100479126, 0.03217557445168495, 0.05709041282534599, 0.0006260537775233388, 0.060490965843200684, 0.04933161661028862, 0.0717652291059494, 0.07864096760749817, 0.007506369147449732, 0.08257804811000824, 0.0020423787645995617, 0.03632594645023346, 0.06585823744535446, 0.049757879227399826, 0.04135887697339058, 0.10719718784093857, 0.051058329641819, 0.06430868804454803, 0.06367958337068558, 0.05094432830810547, 0.04239531606435776, 0.044474244117736816, 0.034648943692445755, 0.05303168296813965, 0.021759649738669395, 0.06301159411668777, 0.06938421726226807, 0.12174288183450699, 0.008494219742715359, 0.05185634642839432, 8.046627044677734e-06, 0.07328429073095322, 0.10684622824192047, 0.05694274231791496, 0.014936337247490883, 0.03315383940935135, 0.11932369321584702, 0.09877508878707886, 0.05520164966583252, 0.060781240463256836, 0.004960671067237854, 0.04051412642002106, 0.0790150985121727, 0.07098174840211868, 0.11034547537565231, 0.012185811996459961, 0.001992594450712204, 0.05026650428771973, 0.04816662520170212, 0.08558672666549683, 0.058172453194856644, 0.08806802332401276, 0.15289650857448578, 0.07718133926391602, 0.061164602637290955, 0.043299417942762375, 0.014616934582591057, 0.12701667845249176, 0.031345903873443604, 0.05412700027227402, 0.16702398657798767, 0.0701664388179779, 0.035104330629110336, 0.026520704850554466, 0.058038800954818726, 0.07055270671844482, 0.14173422753810883, 0.07558104395866394, 0.04806195944547653, 0.06602955609560013, 0.05252605304121971, 0.0, 0.04723518341779709, 0.07474459707736969, 0.08601193875074387, 0.02801169827580452, 0.034212566912174225, 0.05905865877866745, 0.06937452405691147, 0.08407457172870636, 0.0418599396944046, 0.06993496417999268, 0.10599178075790405, 0.0014764070510864258, 0.0031884924974292517, 0.0, 0.05338595435023308, 0.06440439820289612, 0.05459534376859665, 0.09721386432647705, 0.0008379220962524414, 0.03530815616250038, 0.06500022113323212, 0.0559418722987175, 0.027933523058891296, 0.044344838708639145, 0.003793352050706744, 0.0281950905919075, 0.02645057439804077, 0.031646668910980225, 0.0663449764251709, 0.06601829081773758, 0.04644140601158142, 0.05031461641192436, 0.089027039706707, 0.1249023824930191, 0.08077144622802734, 0.00627312483265996, 0.006602668669074774, 0.02657794952392578, 0.09997563809156418, 0.1097138449549675, 0.10316896438598633, 0.07556693255901337, 0.031804345548152924, 0.046631429344415665, 0.013616045005619526, 0.046595290303230286, 0.06387011706829071, 0.04068392515182495, 0.00039892076165415347, 0.04098522663116455, 0.05911048874258995, 0.03544354438781738, 0.14199760556221008, 0.037081290036439896, 0.04193403199315071, 0.019940780475735664, 0.08920377492904663, 0.07115882635116577, 0.07824142277240753, 0.07815121859312057, 0.023612678050994873, 0.017048249021172523, 0.03505837917327881, 0.10378243029117584, 0.047781817615032196, 0.03888458013534546, 0.08345745503902435, 0.04805034026503563, 0.053460944443941116, 0.05213754624128342, 0.09917199611663818, 0.10151514410972595, 0.09501254558563232, 0.05743621662259102, 0.07454045861959457, 0.07474929839372635, 0.0022422843612730503, 0.053879264742136, 0.014676554128527641, 0.016855496913194656, 0.033414434641599655, 0.07875234633684158, 0.04221630096435547, 0.06088510528206825, 0.04402988404035568, 0.09021218121051788, 0.032826438546180725, 0.07455067336559296, 0.06266999244689941, 0.032231125980615616, 0.04198899120092392, 0.5354360342025757, 0.23979032039642334, 0.11217717081308365, 0.1043408066034317, 0.24282057583332062, 0.40468794107437134, 0.22007636725902557, 0.5062130093574524, 0.3453766703605652, 0.32955336570739746, 0.3978966772556305, 0.07970995455980301, 0.11499322950839996, 0.3982866704463959, 0.3043871521949768, 0.2223607897758484, 0.3167545199394226, 0.30895498394966125, 0.4604819416999817, 0.423267126083374, 0.32253310084342957, 0.25362053513526917, 0.17075946927070618, 0.4907762110233307, 0.14986369013786316, 0.39364326000213623, 0.36229658126831055, 0.28373339772224426, 0.2545703053474426, 0.2727756202220917, 0.6553326845169067, 0.28265970945358276, 0.46913549304008484, 0.22123153507709503, 0.11733731627464294, 0.23816552758216858, 0.14531448483467102, 0.6433504819869995, 0.2966630458831787, 0.40188348293304443, 0.34777384996414185, 0.3036677837371826, 0.6066943407058716, 0.2555936574935913, 0.36825117468833923, 0.04076537862420082, 0.14691489934921265, 0.357464998960495, 0.6068562865257263, 0.4269474446773529, 0.4017312526702881, 0.320951372385025, 0.4291316270828247, 0.07779093831777573, 0.3193786144256592, 0.3544849455356598, 0.18579129874706268, 0.3170951306819916, 0.08788064867258072, 0.4124268591403961, 0.2503376007080078, 0.4552236795425415, 0.43805810809135437, 0.27499157190322876, 0.5508751273155212, 0.1850200742483139, 0.7548182606697083, 0.4513733983039856, 0.15755505859851837, 0.45127126574516296, 0.17511431872844696, 0.27655696868896484, 0.41923004388809204, 0.6732339262962341, 0.2345537394285202, 0.6023862957954407, 0.37537455558776855, 0.5137651562690735, 0.1605749875307083, 0.35312628746032715, 0.4609432816505432, 0.6884902715682983, 0.24097445607185364, 0.3369022309780121, 0.20153649151325226, 0.38953056931495667, 0.1302288919687271, 0.2499724179506302, 0.3211522698402405, 0.18015654385089874, 0.22416411340236664, 0.34779661893844604, 0.45412030816078186, 0.31023919582366943, 0.4026375114917755, 0.5386137366294861, 0.40665507316589355, 0.31227123737335205, 0.211715966463089, 0.3191453516483307, 0.3309497833251953, 0.24563530087471008, 0.3149535059928894, 0.2900904417037964, 0.3852717876434326, 0.20183108747005463, 0.5615346431732178, 0.5668832063674927, 0.13853679597377777, 0.4259341359138489, 0.43677350878715515, 0.1722077578306198, 0.23695556819438934, 0.2756512463092804, 0.38086357712745667, 0.09022540599107742, 0.006679350044578314, 0.30115699768066406, 0.3345731794834137, 0.3594731092453003, 0.4984666407108307, 0.454641193151474, 0.40213701128959656, 0.4946835935115814, 0.46981802582740784, 0.6818068027496338, 0.5118770599365234, 0.4991409182548523, 0.2458893209695816, 0.4243386685848236, 0.5874561667442322, 0.39970046281814575, 0.5193523168563843, 0.25374147295951843, 0.1207035630941391, 0.20618394017219543, 0.1256912797689438, 0.5719172358512878, 0.3942793309688568, 0.2676447629928589, 0.2325485497713089, 0.5931475162506104, 0.45206958055496216, 0.08708389103412628, 0.2240571528673172, 0.4953795373439789, 0.37538591027259827, 0.45632293820381165, 0.13245050609111786, 0.4435740113258362, 0.21221838891506195, 0.5567967891693115, 0.22625687718391418, 0.1480351984500885, 0.48833590745925903, 0.5133153200149536, 0.3742242455482483, 0.19253914058208466, 0.3484249711036682, 0.2999247610569, 0.44000953435897827, 0.3365170955657959, 0.18649570643901825, 0.551913321018219, 0.3531647324562073, 0.25488749146461487, 0.18253858387470245, 0.4266709089279175, 0.4185810685157776, 0.28958550095558167, 0.22814929485321045, 0.4456709325313568, 0.17831873893737793, 0.41566553711891174, 0.3413424491882324, 0.29119768738746643, 0.25927433371543884, 0.38305044174194336, 0.2958604693412781, 0.23568277060985565, 0.8237754702568054, 0.3928843140602112, 0.2941036820411682, 0.3487158417701721, 0.18109703063964844, 0.2838733196258545, 0.19061793386936188, 0.3559211790561676, 0.3214881420135498, 0.11908689141273499, 0.29028114676475525, 0.5761349201202393, 0.2172292023897171, 0.3903122544288635, 0.32368651032447815, 0.6176082491874695, 0.4035172164440155, 0.2215849608182907, 0.3331918716430664, 0.18807440996170044, 0.16464057564735413, 0.23822085559368134, 0.18451622128486633, 0.346557080745697, 0.3512616753578186, 0.1979571431875229, 0.15788483619689941, 0.804472804069519, 0.22995208203792572, 0.10289010405540466, 0.2615431547164917, 0.2670995891094208, 0.18414942920207977, 0.4270166754722595, 0.4039037227630615, 0.21047306060791016, 0.08077694475650787, 0.17595675587654114, 0.2503950297832489, 0.17835600674152374, 0.1466159075498581, 0.4759705662727356, 0.5946718454360962, 0.4677335321903229, 0.2860576808452606, 0.26381418108940125, 0.4334215521812439, 0.07914412766695023, 0.3268074095249176, 0.2954067587852478, 0.42890700697898865, 0.28639909625053406, 0.4010646343231201, 0.40716367959976196, 0.27883657813072205, 0.5891413688659668, 0.5916471481323242, 0.33276283740997314, 0.4742860794067383, 0.30042603611946106, 0.3738284111022949, 0.4193459153175354, 0.39674896001815796, 0.10779545456171036, 0.27953392267227173, 0.8218289613723755, 0.24535603821277618, 0.2669932544231415, 0.06754230707883835, 0.6527155041694641, 0.1683996617794037, 0.21881182491779327, 0.4422770142555237, 0.1119953989982605, 0.32827872037887573, 0.21762368083000183, 0.527481198310852, 0.5346364974975586, 0.16583570837974548, 0.316821426153183, 0.22670204937458038, 0.36273086071014404, 0.09253311157226562, 0.33180925250053406, 0.4818611145019531, 0.0821516290307045, 0.35559141635894775, 0.4663654863834381, 0.5924111604690552, 0.27489662170410156, 0.23619601130485535, 0.8092939853668213, 0.7423622012138367, 0.378834068775177, 0.23821838200092316, 0.7105935215950012, 0.4719912111759186, 0.23138141632080078, 0.39735159277915955, 0.2941904067993164, 0.734505295753479, 0.3121468424797058, 0.20385493338108063, 0.1709948629140854, 0.4675009846687317, 0.4862467348575592, 0.6137627363204956, 0.4667362868785858, 0.33247771859169006, 0.1332465261220932, 0.17112956941127777, 0.32466191053390503, 0.16112704575061798, 0.2061573714017868, 0.29463058710098267, 0.23186953365802765, 0.274255633354187, 0.630848228931427, 0.7084805369377136, 0.36453574895858765, 38.29649353027344, 72.059326171875, 30.467498779296875, 40.87361145019531, 64.73609924316406, 20.16961669921875, 27.606868743896484, 10.416839599609375, 10.99906063079834, 25.452177047729492, 16.70118522644043, 19.30511474609375, 11.969696044921875, 59.9932861328125, 13.3651123046875, 17.97589111328125, 6.8554229736328125, 53.02927780151367, 28.057157516479492, 56.6818733215332, 7.457305908203125, 21.974655151367188, 8.995716094970703, 16.806617736816406, 26.23520278930664, 8.067718505859375, 101.91728973388672, 14.72021484375, 24.269744873046875, 8.3543701171875, 19.66520881652832, 7.899612903594971, 24.007606506347656, 22.101600646972656, 50.12354278564453, 20.60633659362793, 23.970138549804688, 56.424560546875, 13.643263816833496, 16.887712478637695, 15.642570495605469, 47.936370849609375, 27.774248123168945, 12.813995361328125, 11.416417121887207, 26.66009521484375, 13.322105407714844, 72.586669921875, 23.68641471862793, 17.30384635925293, 29.27107810974121, 16.38398551940918, 29.212875366210938, 11.237472534179688, 16.709270477294922, 32.583251953125, 14.17740249633789, 33.83314514160156, 17.234146118164062, 17.78641128540039, 7.496174335479736, 27.76252555847168, 22.363510131835938, 23.49420928955078, 40.02973937988281, 10.8914794921875, 49.52644348144531, 80.5723876953125, 20.059432983398438, 56.34852600097656, 40.50820541381836, 26.325912475585938, 14.326027870178223, 27.487689971923828, 25.539520263671875, 31.281503677368164, 65.10189819335938, 6.986114978790283, 26.965421676635742, 30.10951042175293, 13.805877685546875, 16.064010620117188, 12.299684524536133, 16.965747833251953, 8.417831420898438, 28.073339462280273, 23.549407958984375, 19.55476188659668, 13.295654296875, 86.3105239868164, 9.069290161132812, 9.017959594726562, 30.613588333129883, 14.149985313415527, 27.516828536987305, 27.058185577392578, 21.369140625, 18.506752014160156, 15.68489933013916, 63.98914337158203, 10.149614334106445, 15.119293212890625, 18.37012481689453, 34.19978332519531, 24.47697639465332, 46.17163848876953, 72.86842346191406, 25.60483741760254, 38.16703414916992, 17.121234893798828, 11.980827331542969, 15.431503295898438, 29.510311126708984, 11.078871726989746, 89.61994934082031, 47.1601448059082, 18.00843620300293, 27.32208251953125, 16.886817932128906, 82.7379379272461, 62.985755920410156, 16.180559158325195, 8.578301429748535, 29.58734130859375, 14.6373291015625, 26.847869873046875, 40.08926010131836, 7.041778564453125, 22.980741500854492, 23.246328353881836, 17.728517532348633, 35.42990493774414, 12.30169677734375, 25.201147079467773, 11.81723690032959, 23.61250114440918, 44.016693115234375, 38.699222564697266, 15.07421875, 24.87504005432129, 24.469589233398438, 32.282161712646484, 50.46967315673828, 18.69287872314453, 27.619291305541992, 44.80385208129883, 36.66184997558594, 54.2177734375, 16.630361557006836, 27.51323127746582, 40.5298957824707, 41.36688995361328, 33.21867370605469, 29.718902587890625, 35.43079376220703, 23.79835319519043, 10.751708984375, 25.62908363342285, 17.72015380859375, 39.90557861328125, 15.025299072265625, 50.93147277832031, 21.46207046508789, 38.1849365234375, 24.443614959716797, 24.72627830505371, 17.769065856933594, 13.000030517578125, 19.627471923828125, 16.04871368408203, 48.83393478393555, 12.046905517578125, 10.80426025390625, 48.17820358276367, 70.36101531982422, 29.89773941040039, 22.091644287109375, 52.287933349609375, 11.129300117492676, 11.016280174255371, 46.08061599731445, 10.259796142578125, 47.62434387207031, 18.54296875, 43.378753662109375, 32.424930572509766, 13.674208641052246, 16.110416412353516, 36.890380859375, 37.65884017944336, 30.693254470825195, 45.57879638671875, 10.095352172851562, 10.847382545471191, 32.31585693359375, 10.444961547851562, 27.059720993041992, 5.493743896484375, 40.282684326171875, 21.783964157104492, 8.209442138671875, 15.763816833496094, 17.932600021362305, 37.55317306518555, 21.817440032958984, 12.4678955078125, 58.56916809082031, 20.172014236450195, 16.542179107666016, 35.44887924194336, 59.40720748901367, 9.262771606445312, 14.18175983428955, 36.66262435913086, 33.49101257324219, 19.164688110351562, 11.468528747558594, 13.516485214233398, 21.11627197265625, 51.62092590332031, 50.60833740234375, 10.628188133239746, 8.171573638916016, 59.86623764038086, 16.611541748046875, 43.84788131713867, 23.43922233581543, 40.75403594970703, 41.28228759765625, 26.790061950683594, 55.67132568359375, 24.480253219604492, 43.02052688598633, 21.980106353759766, 39.03900146484375, 33.52520751953125, 13.298370361328125, 17.653961181640625, 19.241683959960938, 10.744596481323242, 36.42835998535156, 31.685522079467773, 14.694602012634277, 13.540756225585938, 50.46267318725586, 42.03045654296875, 8.606231689453125, 26.423797607421875, 14.098925590515137, 28.252342224121094, 25.111862182617188, 50.567840576171875, 96.90605926513672, 83.93339538574219, 127.91648864746094, 38.156150817871094, 47.58203887939453, 21.59207534790039, 6.145020484924316, 16.305973052978516, 35.24029541015625, 26.940458297729492, 18.56170654296875, 10.275527000427246, 56.90325164794922, 9.420654296875, 21.221708297729492, 24.996450424194336, 13.06396484375, 15.150897026062012, 28.21368408203125, 8.494744300842285, 42.57231521606445, 45.82098388671875, 10.508331298828125, 22.039413452148438, 42.61228942871094, 8.1688232421875, 51.12431716918945, 27.788818359375, 38.456871032714844, 17.31475830078125, 15.704726219177246, 73.83854675292969, 30.320404052734375, 41.15338897705078, 19.58238983154297, 15.619384765625, 19.087636947631836, 23.19158935546875, 12.568710327148438, 68.3073501586914, 18.78639793395996, 13.849166870117188, 5.2249908447265625, 7.381591796875, 20.1773681640625, 9.081695556640625, 35.710662841796875, 54.182674407958984, 3.1289610862731934, 1.452401041984558, 1.6708937883377075, 0.9065980315208435, 2.5548019409179688, 1.3070544004440308, 3.37899112701416, 1.7861183881759644, 1.6003408432006836, 1.5529588460922241, 1.704463005065918, 1.3385262489318848, 1.4364449977874756, 1.8834457397460938, 1.5183953046798706, 1.6615324020385742, 1.8383283615112305, 2.3090810775756836, 1.938015103340149, 3.3997442722320557, 1.9103275537490845, 1.2782753705978394, 1.5975708961486816, 2.6785295009613037, 1.4318578243255615, 1.640364646911621, 1.899283528327942, 1.9765455722808838, 1.952096700668335, 2.4054436683654785, 2.248035430908203, 2.5485942363739014, 2.24981427192688, 2.045625686645508, 1.601405143737793, 2.2917404174804688, 1.3008806705474854, 1.5201584100723267, 1.9086217880249023, 1.8606925010681152, 2.1956818103790283, 1.4022248983383179, 2.0753090381622314, 1.0713268518447876, 2.7388885021209717, 2.071974992752075, 2.2176733016967773, 2.3920958042144775, 2.053910255432129, 2.1191587448120117, 1.375096082687378, 2.9920058250427246, 0.6646050810813904, 0.7518917918205261, 1.9315265417099, 1.4852731227874756, 1.0202162265777588, 1.6226357221603394, 1.3617985248565674, 3.0062153339385986, 1.364112377166748, 0.9681176543235779, 2.109832525253296, 2.537881374359131, 2.6890177726745605, 1.1707390546798706, 1.3545873165130615, 1.5129061937332153, 2.0976128578186035, 1.0488348007202148, 3.0161564350128174, 1.6453137397766113, 1.7022199630737305, 1.7581586837768555, 1.0077483654022217, 1.4936920404434204, 2.6595675945281982, 1.5651321411132812, 1.9985768795013428, 1.2287567853927612, 1.18999183177948, 1.0755677223205566, 2.5080387592315674, 2.1864917278289795, 1.5389132499694824, 1.0733968019485474, 1.9761953353881836, 2.418083667755127, 1.3199145793914795, 1.773655652999878, 1.855202555656433, 1.4948662519454956, 2.9515318870544434, 1.184731364250183, 1.7895421981811523, 1.2897461652755737, 2.1800522804260254, 2.1539316177368164, 2.2969236373901367, 1.8348040580749512, 2.176689624786377, 1.5154732465744019, 2.175339937210083, 1.866578459739685, 2.384357452392578, 1.3731716871261597, 1.6382827758789062, 1.1186383962631226, 2.397490978240967, 2.471247673034668, 0.7703601717948914, 1.7345110177993774, 1.5670326948165894, 1.5154086351394653, 1.2419365644454956, 2.097804069519043, 0.9140806198120117, 1.4434021711349487, 1.369845986366272, 1.443276286125183, 1.036421537399292, 1.9908188581466675, 1.0298738479614258, 1.5417804718017578, 1.8595348596572876, 1.510099172592163, 1.0748480558395386, 1.4346494674682617, 2.160719871520996, 1.5272821187973022, 1.1982299089431763, 1.7367684841156006, 2.534503698348999, 0.874041736125946, 1.0435651540756226, 1.9087698459625244, 1.7148313522338867, 1.767269253730774, 1.4466848373413086, 1.814131736755371, 1.2383575439453125, 2.3265068531036377, 2.037825345993042, 1.0047463178634644, 1.9674166440963745, 1.4791351556777954, 1.977366328239441, 1.002795696258545, 1.5711411237716675, 1.4759483337402344, 1.0420403480529785, 2.4717206954956055, 2.5897815227508545, 1.8911370038986206, 1.8215155601501465, 1.6952238082885742, 2.08272385597229, 1.2501440048217773, 2.2294745445251465, 1.4131498336791992, 1.5785988569259644, 2.3584649562835693, 1.8628110885620117, 1.841610312461853, 2.4405455589294434, 3.2743101119995117, 1.141785979270935, 2.6686816215515137, 1.467463493347168, 1.9931397438049316, 2.5033578872680664, 3.029629945755005, 1.2221776247024536, 1.2550934553146362, 2.3152568340301514, 1.5784378051757812, 1.8336690664291382, 1.4981609582901, 1.0439977645874023, 1.5333229303359985, 2.5324337482452393, 1.6723603010177612, 1.8128423690795898, 1.8346936702728271, 1.3886994123458862, 1.9407551288604736, 2.3516290187835693, 1.51162850856781, 0.9464828968048096, 1.5903619527816772, 1.306679606437683, 2.78869366645813, 1.722495436668396, 2.445819139480591, 1.3809212446212769, 2.75101375579834, 1.8597817420959473, 1.4380213022232056, 2.7808446884155273, 1.6981818675994873, 1.63945734500885, 2.4309909343719482, 1.758486270904541, 2.173363208770752, 2.0950636863708496, 2.0334601402282715, 3.0914993286132812, 1.856240153312683, 1.5591732263565063, 1.4959969520568848, 1.9487239122390747, 2.7990972995758057, 2.513278007507324, 1.3018052577972412, 2.2020788192749023, 1.5460827350616455, 1.935679316520691, 3.599830150604248, 2.1609926223754883, 2.1370019912719727, 1.5081413984298706, 1.723280906677246, 1.291406512260437, 1.9155160188674927, 2.147408962249756, 1.2943215370178223, 2.5889391899108887, 2.103123664855957, 0.9843015670776367, 1.7956866025924683, 1.6846158504486084, 2.6512060165405273, 2.2475087642669678, 3.0084946155548096, 1.852518081665039, 2.9071264266967773, 1.2826566696166992, 2.336954355239868, 1.3680771589279175, 1.3726052045822144, 2.162362813949585, 1.5533475875854492, 1.2787246704101562, 2.5782952308654785, 2.696605682373047, 1.7203985452651978, 2.3132808208465576, 2.5138940811157227, 1.871394157409668, 2.831371307373047, 1.1100128889083862, 1.3330645561218262, 1.0519914627075195, 1.8212783336639404, 1.7336817979812622, 1.2019457817077637, 2.4180612564086914, 0.9411648511886597, 1.1818969249725342, 2.2707338333129883, 2.027975082397461, 1.947471022605896, 1.4876751899719238, 2.380948066711426, 2.0855002403259277, 2.003331184387207, 2.9864485263824463, 2.581512689590454, 1.0943603515625, 1.6352789402008057, 1.396296501159668, 2.5426206588745117, 1.1507481336593628, 1.6894387006759644, 2.266054630279541, 3.6027159690856934, 1.9567941427230835, 1.988306999206543, 1.3446320295333862, 1.7547643184661865, 1.8498449325561523, 0.8503646850585938, 2.6683549880981445, 1.4194326400756836, 2.2376585006713867, 1.6506118774414062, 1.7791152000427246, 0.2396998107433319, 2.011418342590332, 1.9958678483963013, 1.5199651718139648, 1.5697659254074097, 1.211798071861267, 2.273813486099243, 1.7973265647888184, 2.3031113147735596, 2.160050392150879, 1.3016653060913086, 1.6650381088256836, 2.6318576335906982, 0.07059967517852783, 0.022355688735842705, 0.14756743609905243, 0.04911818355321884, 0.08032751083374023, 0.07712090015411377, 0.07443942129611969, 0.0007295161485671997, 0.05548420920968056, 0.05967578664422035, 0.0022620547097176313, 0.02520907297730446, 0.00814936775714159, 0.006257493514567614, 0.045658137649297714, 2.1542906324611977e-05, 0.10105844587087631, 0.017046334221959114, 0.03745783865451813, 0.04242432489991188, 0.12811574339866638, 0.16116023063659668, 0.06127294525504112, 0.17019790410995483, 0.057722050696611404, 0.0031260859686881304, 0.011801239103078842, 0.06641720235347748, 0.002273829421028495, 0.036882560700178146, 0.09115945547819138, 0.034590013325214386, 0.0790187194943428, 0.11782463639974594, 0.111831434071064, 0.07065226137638092, 0.1566184163093567, 0.03301924467086792, 0.06647468358278275, 0.030766131356358528, 0.05652075633406639, 0.03558438643813133, 0.025496186688542366, 0.06604509055614471, 0.0006941044121049345, 0.044453591108322144, 0.016519809141755104, 0.05605519562959671, 0.06433524191379547, 0.029034385457634926, 0.12680912017822266, 0.06266026943922043, 0.022422973066568375, 0.08181966841220856, 0.10420188307762146, 0.12846827507019043, 0.11383046954870224, 0.07214980572462082, 0.046142976731061935, 0.04144570231437683, 0.016274793073534966, 0.03519991412758827, 0.047445766627788544, 0.057850491255521774, 0.02461557276546955, 0.0688546672463417, 0.06163347512483597, 0.0604860894382, 0.08891485631465912, 0.0763687863945961, 0.07596773654222488, 0.046630047261714935, 0.05882985144853592, 0.020451795309782028, 0.09187829494476318, 0.049571674317121506, 0.11136304587125778, 0.148766428232193, 0.053898341953754425, 0.0, 0.05137668922543526, 0.11341125518083572, 0.0637989193201065, 0.040013544261455536, 0.0703388899564743, 0.03074871003627777, 0.01851820945739746, 0.05227549001574516, 0.0841016173362732, 0.07977241277694702, 0.03326869010925293, 0.021032273769378662, 0.10077451169490814, 0.06982028484344482, 0.09448076039552689, 0.05740787461400032, 0.038219284266233444, 0.09143491834402084, 0.0806111991405487, 0.03789597004652023, 0.10387399792671204, 0.10170251876115799, 0.07167503982782364, 0.07328443974256516, 0.020032532513141632, 0.16250725090503693, 0.08566241711378098, 0.09040995687246323, 0.09070495516061783, 0.12087102979421616, 0.011705935001373291, 0.07556392252445221, 0.028833508491516113, 0.08929300308227539, 0.04753154516220093, 0.03671669214963913, 0.0814703181385994, 0.0991375744342804, 0.0038744674529880285, 0.06072305515408516, 0.05089914798736572, 0.007451939862221479, 0.07219141721725464, 0.006172548979520798, 0.12035446614027023, 0.0016193449264392257, 0.12153055518865585, 0.08517950773239136, 0.057998452335596085, 0.10419605672359467, 0.0961068868637085, 0.06617748737335205, 0.055586472153663635, 0.10327877104282379, 0.12230268865823746, 0.009049582295119762, 0.04160507023334503, 0.06046248599886894, 0.08019443601369858, 0.04524897411465645, 0.07959955930709839, 0.07568901777267456, 0.061041295528411865, 0.06406676769256592, 0.04931157827377319, 0.05208677053451538, 0.03792905807495117, 0.0, 0.055049724876880646, 0.07712830603122711, 0.00393416453152895, 0.10631749778985977, 0.057489145547151566, 0.023965181782841682, 0.04965123161673546, 0.0, 0.06156039983034134, 0.059168700128793716, 0.05856715142726898, 0.05775849148631096, 0.05278897285461426, 0.06606854498386383, 0.07387077808380127, 0.08235614746809006, 0.07330360263586044, 0.04189572110772133, 0.0459308885037899, 0.020002469420433044, 0.072319895029068, 0.012642443180084229, 0.024072257801890373, 0.11933004856109619, 0.018021468073129654, 0.03792821615934372, 0.019858771935105324, 0.024343611672520638, 0.000905275926925242, 0.12962225079536438, 0.048520803451538086, 0.05094432830810547, 0.01460680365562439, 0.06119797006249428, 0.02577686309814453, 0.014562904834747314, 0.07641652226448059, 0.06586064398288727, 0.04117158427834511, 0.08093129843473434, 0.0006994646391831338, 0.0384749174118042, 0.024134907871484756, 0.026989877223968506, 0.04550304263830185, 0.027494927868247032, 0.11021315306425095, 0.04313584417104721, 0.05468781292438507, 0.001986891031265259, 0.11996448040008545, 0.0612749382853508, 0.03469420596957207, 0.056584682315588, 0.13292832672595978, 0.011231822893023491, 0.04269462451338768, 0.06355341523885727, 0.14442716538906097, 0.02645057439804077, 0.09804931282997131, 0.05839909240603447, 0.11915680766105652, 0.05793626606464386, 0.11981254070997238, 0.10846071690320969, 0.0872788205742836, 0.10378340631723404, 0.03457707166671753, 0.05531418323516846, 0.05409619212150574, 0.014367343857884407, 0.06184742972254753, 0.0019978571217507124, 0.08971314877271652, 0.08950752019882202, 0.09194670617580414, 0.029684705659747124, 0.0631331130862236, 0.030502619221806526, 0.00039869427564553916, 0.12050586193799973, 0.07637346535921097, 0.020523933693766594, 0.0018688010750338435, 0.0484752357006073, 0.044835854321718216, 0.05371452867984772, 3.612518048612401e-05, 0.0284552164375782, 0.026119951158761978, 0.041767239570617676, 0.07026445865631104, 0.055216092616319656, 0.03270214796066284, 0.06821775436401367, 0.06256607174873352, 0.004919565748423338, 0.09649266302585602, 0.005964743904769421, 0.05073317885398865, 0.1140318438410759, 0.03752797842025757, 0.046432044357061386, 0.05849016085267067, 0.08730492740869522, 0.11543738842010498, 0.058974266052246094, 0.09678369015455246, 0.103280209004879, 0.026126375421881676, 0.05979324132204056, 0.06838679313659668, 0.04783029481768608, 0.06916920840740204, 0.04693186283111572, 0.018742704764008522, 0.0010057431645691395, 0.11257722973823547, 0.10187617689371109, 0.14135470986366272, 0.05321221053600311, 0.04707097262144089, 0.010709119029343128, 0.06428248435258865, 0.06002926826477051, 0.08743001520633698, 0.07408073544502258, 0.033437084406614304, 0.05303235724568367, 0.06146794557571411, 0.04669483006000519, 0.0743565559387207, 0.10482320189476013, 0.1328793317079544, 0.025592556223273277, 0.032175324857234955, 0.0744890570640564, 0.0945466011762619, 0.04304707422852516, 0.1436753273010254, 0.00316546019166708, 0.06271939724683762, 0.007025483530014753, 0.09756260365247726, 0.05472784861922264, 0.0042953831143677235, 0.03440225124359131, 0.09582829475402832, 0.08652514219284058, 0.05833340436220169, 0.00017234444385394454, 0.1538330763578415, 0.2761750817298889, 0.6003456711769104, 0.17815783619880676, 0.467047780752182, 0.24969035387039185, 0.5111377239227295, 0.6791425943374634, 0.4172801077365875, 0.33623620867729187, 0.12434783577919006, 0.30308961868286133, 0.6456255912780762, 0.4429244101047516, 0.15601743757724762, 0.5659628510475159, 0.24817202985286713, 0.5330895781517029, 0.1909397393465042, 0.5839871168136597, 0.27876460552215576, 0.35786744952201843, 0.5896603465080261, 0.23607884347438812, 0.07555074244737625, 0.23348191380500793, 0.3650255501270294, 0.6470018029212952, 0.35433730483055115, 0.15579406917095184, 0.3516189455986023, 0.24475622177124023, 0.5933241844177246, 0.5309194326400757, 0.4639907777309418, 0.16404032707214355, 0.10027787834405899, 0.33864709734916687, 0.4549897611141205, 0.28408709168434143, 0.3399403691291809, 0.6783467531204224, 0.4088241457939148, 0.217732235789299, 0.2113053798675537, 0.16158080101013184, 0.2013029307126999, 0.30115213990211487, 0.19525329768657684, 0.2542588710784912, 0.4541511535644531, 0.34390345215797424, 0.3266449570655823, 0.5006028413772583, 0.5845960378646851, 0.4564480483531952, 0.43801650404930115, 0.39589014649391174, 0.2578839957714081, 0.5281422138214111, 0.45667874813079834, 0.5661526322364807, 0.45104140043258667, 0.11185480654239655, 0.21333198249340057, 0.4172533452510834, 0.39674216508865356, 0.8543481230735779, 0.41710731387138367, 0.2025488168001175, 0.40927109122276306, 0.6010826230049133, 0.3164631724357605, 0.2170015424489975, 0.3762110769748688, 0.15035352110862732, 0.33407720923423767, 0.31345516443252563, 0.6961715817451477, 0.37374067306518555, 0.4195770025253296, 0.46666982769966125, 0.45460182428359985, 0.23481658101081848, 0.2051273137331009, 0.10991571098566055, 0.538529098033905, 0.5104851126670837, 0.3473665416240692, 0.3018348217010498, 0.5306569337844849, 0.3675699532032013, 0.2730049788951874, 0.20208537578582764, 0.1740598976612091, 0.4060819149017334, 0.40898996591567993, 0.43169891834259033, 0.17928344011306763, 0.37982210516929626, 0.11276280879974365, 0.08673747628927231, 0.5697003602981567, 0.4796461760997772, 0.34574759006500244, 0.47428184747695923, 0.18856921792030334, 0.3117463290691376, 0.5188960433006287, 0.4450792670249939, 0.14908893406391144, 0.45471349358558655, 0.10345301032066345, 0.31525754928588867, 0.44723790884017944, 0.5759406685829163, 0.4071297347545624, 0.3817698061466217, 0.18480181694030762, 0.5886964797973633, 0.4423927962779999, 0.3720793128013611, 0.6805483102798462, 0.17381949722766876, 0.10229011625051498, 0.7077353596687317, 0.20479270815849304, 0.5094089508056641, 0.23623906075954437, 0.23303408920764923, 0.4070940315723419, 0.1770927459001541, 0.4510074555873871, 0.3234032392501831, 0.45760616660118103, 0.6319311857223511, 0.3580758571624756, 0.16699451208114624, 0.32459700107574463, 0.6904309988021851, 0.41173064708709717, 0.7912135124206543, 0.2941089868545532, 0.22408929467201233, 0.42694002389907837, 0.39531707763671875, 0.41694721579551697, 0.2895926237106323, 0.3433437943458557, 0.2930813133716583, 0.34963202476501465, 0.3282378315925598, 0.566517174243927, 0.7788422703742981, 0.7125080823898315, 0.199724018573761, 0.1169317215681076, 0.26129311323165894, 0.42288175225257874, 0.20062163472175598, 0.22727642953395844, 0.30819839239120483, 0.5358058214187622, 0.46357160806655884, 0.41261085867881775, 0.2692224383354187, 0.307024210691452, 0.33540451526641846, 0.39683452248573303, 0.31607484817504883, 0.12057796120643616, 0.3055974245071411, 0.6147621870040894, 0.40990591049194336, 0.5206465125083923, 0.481506884098053, 0.5632398724555969, 0.49866554141044617, 0.16395388543605804, 0.39413100481033325, 0.34360700845718384, 0.21677687764167786, 0.4132792055606842, 0.1771136075258255, 0.43040403723716736, 0.15040776133537292, 0.37440451979637146, 0.6671000719070435, 0.42541348934173584, 0.09631899744272232, 0.4447486400604248, 0.6781579256057739, 0.18172068893909454, 0.4844616949558258, 0.3927477300167084, 0.25472307205200195, 0.460324764251709, 0.39126327633857727, 0.35828128457069397, 0.3480902314186096, 0.35859930515289307, 0.42772790789604187, 0.39581358432769775, 0.2287006378173828, 0.04459932819008827, 0.29415008425712585, 0.5811863541603088, 0.3476971685886383, 0.31204721331596375, 0.34082213044166565, 0.5343059301376343, 0.457325279712677, 0.5403281450271606, 0.171369269490242, 0.29276418685913086, 0.4655155837535858, 0.53885418176651, 0.5886034369468689, 0.15546289086341858, 0.3419567942619324, 0.3491675853729248, 0.1848972588777542, 0.4338507056236267, 0.6520361304283142, 0.26486220955848694, 0.4011899530887604, 0.5464965105056763, 0.3288678526878357, 0.3856554329395294, 0.5153941512107849, 0.3200173079967499, 0.3901912271976471, 0.6152046322822571, 0.5656861662864685, 0.03465661033987999, 0.3320627808570862, 0.26556164026260376, 0.23689055442810059, 0.3184697926044464, 0.8905659914016724, 0.7110313773155212, 0.49821025133132935, 0.2343255877494812, 0.35481706261634827, 0.3914841115474701, 0.5456511974334717, 0.4663558900356293, 0.49569955468177795, 0.21064963936805725, 0.24093253910541534, 0.47745925188064575, 0.3708740174770355, 0.46746015548706055, 0.9415954947471619, 0.4211556017398834, 0.16465002298355103, 0.21984818577766418, 0.26888275146484375, 0.5879948139190674, 0.3090307414531708, 0.4495455026626587, 0.18085792660713196, 0.4693671762943268, 0.7499447464942932, 0.4635641276836395, 0.20669034123420715, 0.09388811886310577, 0.23010440170764923, 0.5724695324897766, 0.18842990696430206, 0.4697154760360718, 0.45470815896987915, 0.3632601797580719, 0.32834768295288086, 0.43116113543510437, 0.4325009882450104, 0.3754097521305084, 0.45611417293548584, 0.6698347330093384, 0.3386487066745758, 0.10413020849227905, 0.42289644479751587, 0.44558173418045044, 0.4522360861301422, 0.37130728363990784, 0.4212666153907776, 0.1355675607919693, 0.4395122528076172, 0.20809701085090637, 0.4684985876083374, 0.29155296087265015, 0.2890898883342743, 0.379404217004776, 0.46585798263549805, 0.22363610565662384, 0.5190443992614746, 0.71566241979599, 0.4410797655582428, 0.5697044730186462, 0.3930826783180237, 24.911102294921875, 64.08627319335938, 26.36055564880371, 18.693130493164062, 33.72986602783203, 21.9649658203125, 19.093610763549805, 30.049291610717773, 24.6898136138916, 42.139495849609375, 18.717315673828125, 22.238868713378906, 31.668588638305664, 8.018471717834473, 52.586238861083984, 44.92298889160156, 17.953163146972656, 38.053802490234375, 31.50151824951172, 16.834758758544922, 17.344085693359375, 54.26821517944336, 11.36288833618164, 92.78199768066406, 13.14654541015625, 41.279869079589844, 58.96168899536133, 18.290870666503906, 40.144554138183594, 59.322322845458984, 41.403709411621094, 24.33228874206543, 7.101837158203125, 26.6031494140625, 43.083553314208984, 68.67205810546875, 42.86765670776367, 15.878814697265625, 28.729286193847656, 43.20530319213867, 5.12261962890625, 18.652284622192383, 51.88886642456055, 51.32655334472656, 78.54995727539062, 11.678664207458496, 34.03145980834961, 23.680404663085938, 23.768600463867188, 28.00916862487793, 9.11038875579834, 30.60638999938965, 47.386077880859375, 14.147478103637695, 11.777664184570312, 34.329071044921875, 31.19138526916504, 11.48392391204834, 19.65198516845703, 40.617523193359375, 30.91438102722168, 14.582551002502441, 22.835641860961914, 20.470260620117188, 25.655073165893555, 18.781810760498047, 19.44476318359375, 20.30024528503418, 34.894927978515625, 38.506065368652344, 25.68678092956543, 20.240402221679688, 12.919418334960938, 14.019332885742188, 125.49466705322266, 23.49006462097168, 44.86404037475586, 25.803695678710938, 15.827262878417969, 19.367544174194336, 8.510551452636719, 13.856642723083496, 21.508148193359375, 12.518798828125, 46.5716552734375, 12.523834228515625, 15.96484375, 28.902694702148438, 19.782487869262695, 67.84735870361328, 20.001937866210938, 12.977800369262695, 25.024574279785156, 49.16328048706055, 32.40249252319336, 41.62760543823242, 66.73991394042969, 38.62709045410156, 11.271740913391113, 66.71281433105469, 38.14948272705078, 36.49453353881836, 9.037191390991211, 9.62384033203125, 9.107513427734375, 73.95917510986328, 34.693180084228516, 26.91020965576172, 43.1455078125, 26.738998413085938, 14.991806030273438, 74.82077026367188, 23.72785186767578, 25.698505401611328, 42.91798782348633, 92.36968231201172, 9.985061645507812, 51.34748840332031, 25.953338623046875, 27.067108154296875, 33.46516418457031, 15.58329963684082, 17.51022720336914, 24.9815673828125, 7.4713897705078125, 34.80007553100586, 39.458953857421875, 76.846435546875, 26.909452438354492, 51.28363037109375, 39.70305633544922, 32.92228698730469, 38.544944763183594, 24.855792999267578, 22.828216552734375, 42.57770919799805, 37.21693420410156, 47.584686279296875, 95.6878662109375, 24.14292335510254, 46.91115951538086, 24.590341567993164, 31.087797164916992, 18.888229370117188, 34.59028625488281, 31.306493759155273, 18.92054557800293, 25.474952697753906, 32.19010925292969, 94.33086395263672, 11.711130142211914, 38.31536865234375, 12.899187088012695, 8.047836303710938, 14.911330223083496, 13.461496353149414, 22.409086227416992, 25.398605346679688, 28.853973388671875, 14.636122703552246, 23.29058837890625, 19.77674674987793, 23.8670654296875, 78.67082214355469, 34.87882614135742, 16.08348846435547, 59.2410888671875, 18.615215301513672, 35.063446044921875, 32.623992919921875, 53.0623664855957, 69.5103759765625, 11.99698543548584, 24.114837646484375, 16.6214599609375, 20.29485511779785, 32.899505615234375, 25.148014068603516, 45.60587692260742, 9.177099227905273, 35.10024642944336, 25.34846305847168, 24.4749755859375, 11.89166259765625, 12.61383056640625, 9.553112983703613, 19.226444244384766, 5.028417110443115, 41.87174606323242, 13.06201171875, 21.22669792175293, 19.417831420898438, 55.994197845458984, 114.10865783691406, 25.7176513671875, 16.735286712646484, 11.7679443359375, 40.169677734375, 21.283172607421875, 29.661161422729492, 52.52166748046875, 21.87786865234375, 51.69242858886719, 9.781051635742188, 21.20233154296875, 52.69525146484375, 78.12907409667969, 53.19200134277344, 34.65545654296875, 51.82450866699219, 28.29498291015625, 7.763275146484375, 40.878387451171875, 51.39504623413086, 30.451444625854492, 25.073593139648438, 46.50197219848633, 11.0262451171875, 65.73129272460938, 17.48438835144043, 14.358001708984375, 34.78900146484375, 16.133216857910156, 14.844408988952637, 18.82893180847168, 14.727767944335938, 54.85793685913086, 37.38246154785156, 8.696572303771973, 22.8377628326416, 30.504440307617188, 20.48298454284668, 43.9960823059082, 18.961610794067383, 9.981613159179688, 13.757147789001465, 24.585323333740234, 70.93977355957031, 14.825373649597168, 16.633466720581055, 40.26062774658203, 23.24074363708496, 19.262237548828125, 43.81211853027344, 27.01484489440918, 17.19582176208496, 21.064132690429688, 25.356910705566406, 44.509765625, 33.00074005126953, 20.44384765625, 51.2896728515625, 72.05339050292969, 98.77095794677734, 50.84131622314453, 37.95734405517578, 7.062149524688721, 28.11370849609375, 21.21323013305664, 7.420367240905762, 17.5244140625, 25.09636878967285, 35.56656265258789, 14.152670860290527, 31.430002212524414, 12.751784324645996, 30.29998779296875, 51.71165084838867, 17.772048950195312, 9.23471736907959, 57.95458984375, 11.522700309753418, 14.9539794921875, 48.390594482421875, 33.712547302246094, 13.152328491210938, 10.375554084777832, 35.30447006225586, 22.20807647705078, 11.47100830078125, 23.97735595703125, 50.839813232421875, 81.82333374023438, 81.51923370361328, 7.043073654174805, 27.265947341918945, 57.12800598144531, 52.97776412963867, 41.37562942504883, 14.697524070739746, 28.921255111694336, 17.898040771484375, 26.16962432861328, 38.558109283447266, 7.749649524688721, 28.3956298828125, 9.38299560546875, 19.89013671875, 38.33808898925781, 20.82880973815918, 1.3531347513198853, 2.07779598236084, 2.4659531116485596, 2.177720785140991, 1.7120511531829834, 1.1809535026550293, 1.6930514574050903, 1.9112824201583862, 1.2640609741210938, 1.7629401683807373, 1.8152397871017456, 1.8791207075119019, 2.0965166091918945, 1.1236602067947388, 1.8131059408187866, 1.0705394744873047, 2.6371726989746094, 2.492302894592285, 2.411680221557617, 1.4072738885879517, 1.526990532875061, 2.341639280319214, 2.268702745437622, 2.4706690311431885, 1.426289439201355, 1.6725667715072632, 1.3586275577545166, 3.1868584156036377, 1.3412944078445435, 1.6605041027069092, 2.482224941253662, 1.777314305305481, 1.2900701761245728, 1.5315587520599365, 2.025327682495117, 1.9069262742996216, 1.5964058637619019, 1.4361152648925781, 1.8725229501724243, 1.2813940048217773, 2.182509422302246, 0.9546003341674805, 1.654183268547058, 1.834700584411621, 1.9197994470596313, 1.450968861579895, 2.3603925704956055, 2.053020477294922, 1.4180465936660767, 2.834291696548462, 0.8181352019309998, 1.4818254709243774, 2.2810564041137695, 1.4143952131271362, 1.6857447624206543, 1.7376089096069336, 1.6302231550216675, 2.2650201320648193, 2.920031785964966, 1.1327943801879883, 2.080469846725464, 2.536139726638794, 1.5289559364318848, 1.5845050811767578, 3.219334602355957, 1.5208120346069336, 2.490553617477417, 1.9289065599441528, 1.8816055059432983, 1.8207002878189087, 1.4754431247711182, 1.3072690963745117, 1.9518771171569824, 1.10161292552948, 1.6354787349700928, 1.0744715929031372, 1.6460541486740112, 1.4733856916427612, 1.5658092498779297, 2.435940742492676, 2.0727953910827637, 1.727142572402954, 1.741179347038269, 1.903369426727295, 2.1110124588012695, 1.9630346298217773, 1.1088229417800903, 1.56798255443573, 3.222463846206665, 1.8249294757843018, 2.0508170127868652, 1.535998821258545, 1.50178062915802, 2.041008949279785, 1.2676172256469727, 1.9199379682540894, 2.056098699569702, 2.0547423362731934, 2.2902777194976807, 1.0512034893035889, 1.863198161125183, 1.603590965270996, 1.9917925596237183, 1.1534491777420044, 2.2458600997924805, 1.5850826501846313, 1.80955970287323, 2.4877424240112305, 1.965065836906433, 1.9542053937911987, 2.304537534713745, 2.232053518295288, 2.204962968826294, 1.9148554801940918, 2.6259193420410156, 1.6318097114562988, 2.5858099460601807, 1.3769193887710571, 2.1253111362457275, 2.3273515701293945, 2.09628963470459, 1.9488476514816284, 1.9325988292694092, 1.1708898544311523, 0.9013146758079529, 1.4814242124557495, 1.9384936094284058, 2.403470039367676, 2.6211352348327637, 2.47556209564209, 1.744057536125183, 1.4528329372406006, 2.052659511566162, 1.88542902469635, 2.235645055770874, 1.3078413009643555, 1.673473834991455, 2.5456912517547607, 1.1238280534744263, 0.9301801919937134, 2.48982834815979, 2.5264978408813477, 3.1695077419281006, 2.1332592964172363, 2.4293606281280518, 1.3080796003341675, 1.716088056564331, 2.0142831802368164, 1.0200837850570679, 2.727811813354492, 2.151726245880127, 1.4538582563400269, 2.039879560470581, 2.03245210647583, 1.9811222553253174, 1.9628573656082153, 2.4531261920928955, 2.3240251541137695, 1.8661812543869019, 1.3898757696151733, 1.475062370300293, 2.4959557056427, 2.821643829345703, 1.591791033744812, 3.3662290573120117, 2.9536807537078857, 3.5435380935668945, 1.609559178352356, 1.8832062482833862, 2.294377088546753, 2.394801378250122, 2.549293041229248, 2.0062594413757324, 1.8873472213745117, 1.2386705875396729, 1.2182669639587402, 2.282547950744629, 2.0819456577301025, 1.795082926750183, 2.77396297454834, 1.117990255355835, 2.3906424045562744, 1.9714651107788086, 1.414866328239441, 1.8692584037780762, 2.07528018951416, 1.1034711599349976, 2.030280828475952, 1.4358892440795898, 1.9644770622253418, 2.5033209323883057, 2.8823606967926025, 2.214235544204712, 2.1709327697753906, 1.9013423919677734, 1.1686162948608398, 1.6879302263259888, 1.9554640054702759, 2.0851964950561523, 1.6952428817749023, 2.0012693405151367, 1.3055967092514038, 0.34975719451904297, 1.820942759513855, 2.1141998767852783, 1.5367287397384644, 2.625375986099243, 1.964272379875183, 1.1819868087768555, 1.5731306076049805, 2.0436105728149414, 2.185305595397949, 1.5578618049621582, 1.6055620908737183, 2.203740119934082, 1.4257426261901855, 1.9612358808517456, 1.9987621307373047, 2.6634302139282227, 2.8807497024536133, 2.1599419116973877, 1.7400610446929932, 1.0617269277572632, 1.667988896369934, 2.507181406021118, 2.3279333114624023, 1.609688639640808, 2.0694398880004883, 1.8082265853881836, 2.3473880290985107, 1.7582024335861206, 2.025244951248169, 1.4573217630386353, 1.7002696990966797, 1.833514928817749, 0.8625840544700623, 2.112931251525879, 1.607888102531433, 2.5300662517547607, 1.824154019355774, 1.728194236755371, 2.434979200363159, 1.5511447191238403, 1.689258337020874, 2.9298183917999268, 1.9323548078536987, 1.95754873752594, 2.9270401000976562, 1.638161301612854, 2.181817054748535, 2.0157809257507324, 1.5862301588058472, 1.9293280839920044, 2.735377073287964, 0.04963035508990288, 2.353846311569214, 1.6751030683517456, 3.223841428756714, 1.917710781097412, 2.670151948928833, 1.2145525217056274, 2.5225582122802734, 1.0666898488998413, 1.191681146621704, 1.7753626108169556, 2.5161232948303223, 2.2260582447052, 3.2236413955688477, 1.1742228269577026, 1.2821455001831055, 1.0048627853393555, 1.2707929611206055, 2.750596284866333, 1.7025972604751587, 2.435845375061035, 1.6126028299331665, 2.565141439437866, 2.984241485595703, 2.082484245300293, 2.5304677486419678, 2.3504130840301514, 1.6651906967163086, 3.0874550342559814, 1.2708102464675903, 2.0151493549346924, 1.2116940021514893, 1.351298451423645, 2.334995985031128, 2.298222541809082, 1.2339309453964233, 2.9829180240631104, 1.486716389656067, 2.080491065979004, 1.2437076568603516, 1.5473793745040894, 1.6968343257904053, 1.9859894514083862, 2.169624090194702, 3.23978328704834, 1.5733269453048706, 0.06851685047149658, 0.013511642813682556, 0.010442376136779785, 0.043253540992736816, 0.09898944944143295, 0.1008208692073822, 0.0, 0.09203268587589264, 0.07904799282550812, 0.04274702072143555, 0.07518093287944794, 0.03356784209609032, 0.060428518801927567, 0.013429734855890274, 0.09828666597604752, 0.07393919676542282, 0.051746487617492676, 0.049480319023132324, 0.056664418429136276, 0.027287423610687256, 0.056390002369880676, 0.07959292083978653, 0.06438593566417694, 0.0908680111169815, 0.05590905249118805, 0.0619027353823185, 0.11615215241909027, 0.02289128303527832, 0.0109712528064847, 0.05147392302751541, 0.16715463995933533, 0.06736044585704803, 0.05475323647260666, 0.09322290867567062, 0.022371329367160797, 0.026384415104985237, 0.08160769939422607, 0.08829089999198914, 0.03731071949005127, 0.10017715394496918, 0.06116954982280731, 0.05644452944397926, 0.11955498158931732, 0.05620986968278885, 0.06412696838378906, 0.06253737956285477, 0.1081024557352066, 0.03703475743532181, 0.03697633743286133, 0.08587408810853958, 0.04791450500488281, 0.07167050242424011, 0.049518730491399765, 0.09556203335523605, 0.1610608696937561, 0.03406006097793579, 0.09637714177370071, 0.08781254291534424, 0.024887189269065857, 0.06820350140333176, 0.056848764419555664, 0.11989117413759232, 0.037450555711984634, 0.09460922330617905, 0.09608321636915207, 0.062396228313446045, 0.06203215569257736, 0.10150955617427826, 0.030828867107629776, 0.03584883734583855, 0.048455893993377686, 0.1382591277360916, 0.11485467851161957, 0.0905163586139679, 0.05506736785173416, 0.009284264408051968, 0.013589506968855858, 0.04296500235795975, 0.03013545833528042, 0.05678701400756836, 0.041448477655649185, 0.08171173185110092, 0.03571624308824539, 0.0859183669090271, 0.05292454734444618, 0.01548356469720602, 0.0102362260222435, 0.012536480091512203, 0.03928312286734581, 0.002896788762882352, 0.04837452247738838, 0.0760645866394043, 0.04812054708600044, 0.024802379310131073, 0.1291092038154602, 0.035968679934740067, 0.0027407698798924685, 0.12601812183856964, 0.04215371981263161, 0.09051042050123215, 0.051683731377124786, 0.10586507618427277, 0.1075231209397316, 0.07103860378265381, 0.028621643781661987, 0.025413990020751953, 0.11095450818538666, 0.06842988729476929, 0.05507518723607063, 0.035752177238464355, 0.059874773025512695, 0.019742552191019058, 0.10221949964761734, 0.07224263995885849, 0.029107870534062386, 0.06381361186504364, 0.035369519144296646, 0.045325517654418945, 0.10865842550992966, 0.07074639946222305, 0.04977044463157654, 0.06339479237794876, 0.11205387115478516, 0.010567188262939453, 0.056629035621881485, 0.06682402640581131, 0.06977424770593643, 0.0781126543879509, 0.024874409660696983, 0.08577181398868561, 0.010272269137203693, 0.061229512095451355, 0.027522515505552292, 0.11533790081739426, 0.10882797092199326, 0.0765518993139267, 0.09017554670572281, 0.033525943756103516, 0.09229405224323273, 0.11087789386510849, 0.06115007400512695, 0.08600150793790817, 0.08416128158569336, 0.016398044303059578, 0.0440715067088604, 0.14244413375854492, 0.10940324515104294, 0.06449412554502487, 0.06932326406240463, 0.057965993881225586, 0.04550493136048317, 0.02000405825674534, 0.07549028098583221, 0.053188059478998184, 0.06861186027526855, 0.07306529581546783, 0.05283040925860405, 0.06898665428161621, 0.033530592918395996, 0.04294891282916069, 0.04213416948914528, 0.1302017718553543, 0.01806509494781494, 0.05961117520928383, 0.07753179967403412, 0.00952393189072609, 0.07764255255460739, 0.030625054612755775, 0.09940219670534134, 0.041157227009534836, 0.08673948049545288, 0.11191331595182419, 0.0847894549369812, 0.027232885360717773, 0.03437042236328125, 0.12296456098556519, 0.07815182209014893, 0.019780341535806656, 0.07105135917663574, 0.0825997069478035, 0.035701487213373184, 0.1040748581290245, 0.04237991198897362, 0.07130169123411179, 0.056211113929748535, 0.058115072548389435, 0.09782571345567703, 0.09647103399038315, 0.11227376759052277, 0.001999277388677001, 0.08344303071498871, 0.07751469314098358, 0.07258257269859314, 0.07742030918598175, 0.08537046611309052, 0.06498873233795166, 0.12221115827560425, 0.05805781111121178, 0.05786300450563431, 0.10504808276891708, 0.09481307864189148, 0.06282562762498856, 0.047828614711761475, 0.09428554028272629, 0.05838269740343094, 0.012286907993257046, 0.03453871235251427, 0.069975346326828, 0.048418980091810226, 0.06156742945313454, 0.05817049741744995, 0.06219583377242088, 0.02952221781015396, 0.09827888011932373, 0.09660699963569641, 0.13564378023147583, 0.06654615700244904, 0.041867952793836594, 0.03627955541014671, 0.073424331843853, 0.06126773729920387, 0.11983872950077057, 0.02789938449859619, 0.08218108862638474, 0.05837744474411011, 0.039890363812446594, 0.02789938449859619, 0.1484338790178299, 0.03303241729736328, 0.10480636358261108, 0.10158904641866684, 0.05847250670194626, 0.09831858426332474, 0.05657762289047241, 0.06130363419651985, 0.0014264201745390892, 0.06975262612104416, 0.06737637519836426, 0.010315777733922005, 0.1488666534423828, 0.0415881872177124, 0.029713334515690804, 0.04041260480880737, 0.050371475517749786, 0.08093961328268051, 0.08352982252836227, 0.07321657240390778, 0.09330272674560547, 0.06034821271896362, 0.11773259937763214, 0.0028831118252128363, 0.07462175190448761, 0.0023505091667175293, 0.09297603368759155, 0.022764315828680992, 0.08550450950860977, 0.042067766189575195, 0.08189340680837631, 0.08049251139163971, 0.0923566222190857, 0.10759133845567703, 0.08874493092298508, 0.09357507526874542, 0.055863261222839355, 0.02974647469818592, 0.050099872052669525, 0.06464207172393799, 0.10827398300170898, 0.08153855055570602, 0.10571488738059998, 0.017502261325716972, 0.07705657929182053, 0.03899536281824112, 0.07280850410461426, 0.06781892478466034, 0.05103931203484535, 0.08580539375543594, 0.029998987913131714, 0.028084639459848404, 0.04248857870697975, 0.07350931316614151, 0.08675903081893921, 0.10357324033975601, 0.09159456193447113, 0.11492201685905457, 0.0619325190782547, 0.014293460175395012, 0.0042357174679636955, 0.025202393531799316, 0.027204567566514015, 0.10516192018985748, 0.060853976756334305, 0.044385891407728195, 0.03971153125166893, 0.07589520514011383, 0.0911344513297081, 0.07899883389472961, 0.08131346851587296, 0.05919161066412926, 0.05278897285461426, 0.3399539887905121, 0.3959364891052246, 0.21353769302368164, 0.3405270278453827, 0.4397073984146118, 0.30101561546325684, 0.6035045981407166, 0.40563011169433594, 0.21873843669891357, 0.5493161082267761, 0.4359957277774811, 0.3866916596889496, 0.46193116903305054, 0.42731109261512756, 0.38452255725860596, 0.3954225778579712, 0.3530772030353546, 0.3728793263435364, 0.3569280803203583, 0.308845579624176, 0.39659690856933594, 0.3843040466308594, 0.3496159315109253, 0.3730087876319885, 0.40537717938423157, 0.4035964906215668, 0.113581083714962, 0.5068074464797974, 0.3899568021297455, 0.3609006404876709, 0.03256632760167122, 0.4617357850074768, 0.6597518920898438, 0.24353140592575073, 0.5902762413024902, 0.28360211849212646, 0.33302775025367737, 0.601887583732605, 0.5796932578086853, 0.008088893257081509, 0.4930155873298645, 0.44798415899276733, 0.4920501708984375, 0.441707968711853, 0.22002942860126495, 0.22760947048664093, 0.39646831154823303, 0.4001881182193756, 0.10522851347923279, 0.31384629011154175, 0.4363372325897217, 0.1852918267250061, 0.4771156311035156, 0.5381032228469849, 0.09450141340494156, 0.43012118339538574, 0.33902841806411743, 0.3440025746822357, 0.4465261995792389, 0.3941095769405365, 0.3227146565914154, 0.19262857735157013, 0.14616651833057404, 0.5333242416381836, 0.34779101610183716, 0.3113517761230469, 0.17900517582893372, 0.277081698179245, 0.5645912885665894, 0.6117187142372131, 0.3177535831928253, 0.5969518423080444, 0.16497328877449036, 0.504124641418457, 0.32092612981796265, 0.407600462436676, 0.5131700038909912, 0.41933774948120117, 0.3452712595462799, 0.5687319040298462, 0.26567500829696655, 0.2701890766620636, 0.3201797902584076, 0.9135094881057739, 0.17264890670776367, 0.595765233039856, 0.2586818337440491, 0.6064088344573975, 0.31839919090270996, 0.2861913740634918, 0.5835569500923157, 0.6402871012687683, 0.32962721586227417, 0.622299313545227, 0.31281036138534546, 0.16255870461463928, 0.44606053829193115, 0.3689304292201996, 0.3627990782260895, 0.3674143850803375, 0.7355764508247375, 0.7099180221557617, 0.5342096090316772, 0.2812516987323761, 0.4242381155490875, 0.44966188073158264, 0.35794463753700256, 0.49684545397758484, 0.18110576272010803, 0.2531624734401703, 0.22962485253810883, 0.4831155240535736, 0.4036569595336914, 0.5404203534126282, 0.5601234436035156, 0.41400381922721863, 0.782662570476532, 0.48360809683799744, 0.4764934480190277, 0.3354657292366028, 0.44375738501548767, 0.1026821881532669, 0.43967825174331665, 0.31807318329811096, 0.2589019238948822, 0.4880503714084625, 0.4732111990451813, 0.22758260369300842, 0.45980849862098694, 0.72491455078125, 0.7408521771430969, 0.20384033024311066, 0.6596927642822266, 0.08329814672470093, 0.2749596834182739, 0.3875015676021576, 0.39023351669311523, 0.40966641902923584, 0.7234123349189758, 0.25890329480171204, 0.32397162914276123, 0.5031546950340271, 0.47726184129714966, 0.2359951287508011, 0.44899022579193115, 0.43349501490592957, 0.24354545772075653, 0.44154348969459534, 0.5190004110336304, 0.662420928478241, 0.5402340292930603, 1.1798564195632935, 0.1998535692691803, 0.8452998399734497, 0.539170503616333, 0.1709354966878891, 0.17451220750808716, 0.30927443504333496, 0.29839181900024414, 0.5840362906455994, 0.3771084249019623, 0.5065730810165405, 0.5588445663452148, 0.5265844464302063, 0.27385663986206055, 0.3857615888118744, 0.2861742079257965, 0.23416216671466827, 0.2858576774597168, 0.36146730184555054, 0.43473875522613525, 0.5436328053474426, 0.6855226159095764, 0.5469775199890137, 0.5565072298049927, 0.31361153721809387, 0.6291577219963074, 0.3227172791957855, 0.30534395575523376, 0.47364431619644165, 0.4483294188976288, 0.17100591957569122, 0.812427818775177, 0.34402427077293396, 0.447610080242157, 0.5084130167961121, 0.5246577858924866, 0.19596248865127563, 0.7243214845657349, 0.17137980461120605, 0.7653980255126953, 0.5686986446380615, 0.8052355647087097, 0.5890681147575378, 0.6046113967895508, 0.4161948561668396, 0.2316529005765915, 0.5571791529655457, 0.27749910950660706, 0.25023365020751953, 0.09928717464208603, 0.18709762394428253, 0.3409087061882019, 0.23079036176204681, 0.6899188160896301, 0.3415396809577942, 0.6244249939918518, 0.18875262141227722, 0.3846456706523895, 0.559151291847229, 0.4070196747779846, 0.16055646538734436, 0.4684329032897949, 0.5406777858734131, 0.4166157841682434, 0.1852353811264038, 0.2934300899505615, 0.4755309820175171, 0.20394812524318695, 0.4197285771369934, 0.8590298891067505, 0.31681039929389954, 0.40410757064819336, 0.27312812209129333, 0.5857768654823303, 0.7135797739028931, 0.6632431745529175, 0.4822961390018463, 0.38187652826309204, 0.4566729664802551, 0.3306991457939148, 0.23296234011650085, 0.4930989742279053, 0.3690086305141449, 0.5013558864593506, 0.45720458030700684, 0.535065233707428, 0.2882176637649536, 0.4987632632255554, 0.7144405841827393, 0.23639646172523499, 0.1717836707830429, 0.3707640767097473, 0.6147233247756958, 0.5779587626457214, 0.30104711651802063, 0.46803155541419983, 0.1939467191696167, 0.5730372667312622, 0.4461754858493805, 0.3345201015472412, 0.25023719668388367, 0.4752886891365051, 0.6360468864440918, 0.10886016488075256, 0.5494035482406616, 0.8199326395988464, 0.7349129915237427, 0.7211715579032898, 0.6046372652053833, 0.7852213978767395, 0.10548269003629684, 0.43693050742149353, 0.15486934781074524, 0.2677779495716095, 0.28106123208999634, 0.43029189109802246, 0.7462916374206543, 0.22907674312591553, 0.350585401058197, 0.2181267887353897, 0.6306940317153931, 0.5530489087104797, 0.4466400742530823, 0.33903923630714417, 0.6933218240737915, 0.40476489067077637, 0.18815520405769348, 0.344979852437973, 0.5322093963623047, 0.17843230068683624, 0.4046957194805145, 0.6331613659858704, 0.18424873054027557, 0.577189028263092, 0.30343055725097656, 0.3308796286582947, 0.017768464982509613, 0.27223271131515503, 0.5129182934761047, 0.40095582604408264, 0.507044792175293, 0.460114061832428, 0.6553385853767395, 0.36357975006103516, 0.18986044824123383, 0.447323203086853, 0.10168717056512833, 0.6096320152282715, 0.3523097038269043, 18.006996154785156, 7.3852715492248535, 11.86236572265625, 10.5760498046875, 35.03694152832031, 69.30793762207031, 62.563533782958984, 40.82278060913086, 29.165639877319336, 10.44586181640625, 24.0211181640625, 19.48923110961914, 35.264007568359375, 121.86541748046875, 32.014976501464844, 33.25733947753906, 27.228422164916992, 12.653006553649902, 38.03645324707031, 18.49207878112793, 37.512908935546875, 29.34052848815918, 34.119476318359375, 24.3389892578125, 110.98099517822266, 16.656005859375, 31.377695083618164, 23.496429443359375, 22.37598991394043, 55.849365234375, 79.11138153076172, 19.56158447265625, 43.26499557495117, 40.45782470703125, 47.84532165527344, 30.058115005493164, 36.806243896484375, 24.91204833984375, 26.239736557006836, 39.15346908569336, 23.606361389160156, 66.4221420288086, 30.657211303710938, 8.508026123046875, 26.941844940185547, 42.271240234375, 14.83290958404541, 9.65435791015625, 37.001922607421875, 9.656494140625, 23.235458374023438, 11.696372032165527, 9.58197021484375, 19.3702392578125, 17.85590934753418, 14.229259490966797, 24.930824279785156, 7.39959716796875, 12.424041748046875, 11.126112937927246, 15.217620849609375, 21.051025390625, 38.09874725341797, 41.4483642578125, 9.124908447265625, 13.67596435546875, 9.92529296875, 17.056182861328125, 24.611051559448242, 48.5634765625, 28.016624450683594, 27.74424171447754, 22.42640495300293, 23.349105834960938, 75.78871154785156, 41.189208984375, 40.53493881225586, 12.588119506835938, 14.632265090942383, 17.35507583618164, 100.01436614990234, 26.6807861328125, 12.893935203552246, 37.9027214050293, 38.94512939453125, 12.12518310546875, 65.54706573486328, 66.2620849609375, 50.95976638793945, 37.79066467285156, 52.6953125, 48.984130859375, 18.487770080566406, 12.914225578308105, 97.65988159179688, 19.351593017578125, 34.28759765625, 14.105727195739746, 12.763580322265625, 21.681686401367188, 10.0789794921875, 9.5460205078125, 27.37274169921875, 62.28273391723633, 33.04763412475586, 48.65171813964844, 76.93025207519531, 34.6939697265625, 23.829635620117188, 10.902360916137695, 33.20197296142578, 10.604728698730469, 21.537111282348633, 28.911922454833984, 38.56205368041992, 27.3538818359375, 19.295595169067383, 32.22885513305664, 39.39487838745117, 39.12896728515625, 35.59463119506836, 31.43255615234375, 58.06435775756836, 23.320716857910156, 35.5496711730957, 9.611823081970215, 12.982436180114746, 24.724609375, 11.76226806640625, 27.87489128112793, 41.098026275634766, 18.05120277404785, 13.483673095703125, 86.48995971679688, 68.15670013427734, 43.984920501708984, 40.316471099853516, 48.543304443359375, 110.29232025146484, 13.160252571105957, 10.289569854736328, 30.220184326171875, 23.065908432006836, 13.249435424804688, 25.83997917175293, 8.560897827148438, 34.6258544921875, 16.2227840423584, 19.52459716796875, 20.066436767578125, 49.99073028564453, 14.471144676208496, 10.994391441345215, 11.125555992126465, 28.32904052734375, 22.176435470581055, 60.56059265136719, 53.77952194213867, 21.65994644165039, 25.72181510925293, 23.67529296875, 77.78021240234375, 30.925594329833984, 42.49072265625, 71.75436401367188, 46.26607131958008, 23.793973922729492, 33.26870346069336, 19.24951171875, 8.097926139831543, 26.738821029663086, 40.110809326171875, 44.536834716796875, 31.83978271484375, 36.38340759277344, 21.881534576416016, 47.66628646850586, 12.847121238708496, 54.915008544921875, 62.05072021484375, 24.37812614440918, 20.07185173034668, 55.2586555480957, 30.464208602905273, 50.59934616088867, 23.659523010253906, 16.331039428710938, 19.15833854675293, 15.0562744140625, 53.50205993652344, 10.920257568359375, 23.526412963867188, 31.63946533203125, 22.625898361206055, 37.757476806640625, 62.83445739746094, 19.051788330078125, 16.581573486328125, 24.19512939453125, 14.534926414489746, 18.45164680480957, 53.49114990234375, 9.21502685546875, 42.43665313720703, 51.34814453125, 26.09268569946289, 18.678110122680664, 44.06348419189453, 61.44453048706055, 52.14345169067383, 118.36234283447266, 13.63397216796875, 46.779052734375, 12.450932502746582, 15.442475318908691, 35.32035446166992, 20.17416763305664, 36.54616928100586, 28.778812408447266, 38.51264190673828, 66.6414566040039, 28.653732299804688, 17.78734588623047, 37.31201934814453, 14.086336135864258, 28.667869567871094, 43.23389434814453, 67.83283996582031, 14.608154296875, 15.261520385742188, 12.676335334777832, 23.069974899291992, 50.16990280151367, 10.988691329956055, 47.78496170043945, 24.80145263671875, 31.94525718688965, 16.03485107421875, 45.65399169921875, 47.40094757080078, 31.946372985839844, 12.356502532958984, 34.20016098022461, 24.83613395690918, 20.540512084960938, 30.183563232421875, 20.8385009765625, 38.947052001953125, 10.265853881835938, 19.743255615234375, 33.244178771972656, 13.313010215759277, 12.404471397399902, 56.86501693725586, 9.107315063476562, 23.74908447265625, 64.207275390625, 10.7642822265625, 30.659774780273438, 21.31732177734375, 69.84538269042969, 16.120880126953125, 20.455184936523438, 48.61720657348633, 9.000701904296875, 14.810378074645996, 12.77044677734375, 9.031204223632812, 18.237945556640625, 9.2054443359375, 12.992963790893555, 76.1376953125, 64.1966552734375, 54.830780029296875, 43.7645263671875, 14.602404594421387, 11.492416381835938, 27.08451271057129, 36.0302734375, 21.497894287109375, 8.599014282226562, 27.655519485473633, 38.57108688354492, 34.02651596069336, 52.49860382080078, 35.6866455078125, 39.71995162963867, 52.17567443847656, 13.589202880859375, 50.58427810668945, 32.16935729980469, 34.694305419921875, 10.992013931274414, 13.70135498046875, 13.845720291137695, 27.670536041259766, 25.617666244506836, 42.93464660644531, 27.30633544921875, 58.370208740234375, 2.732591152191162, 1.670024037361145, 1.8661704063415527, 2.5790374279022217, 0.8836326599121094, 1.4378783702850342, 1.566834568977356, 1.171777367591858, 1.5658254623413086, 1.9448585510253906, 1.7858238220214844, 1.9553955793380737, 2.1633501052856445, 1.6941289901733398, 3.199298143386841, 2.554934501647949, 1.7727056741714478, 2.5658726692199707, 2.8382976055145264, 2.18084716796875, 1.7433781623840332, 2.220330238342285, 2.6567790508270264, 2.6469147205352783, 1.9726672172546387, 3.0700502395629883, 1.244347095489502, 1.710774540901184, 2.3709940910339355, 1.524575114250183, 2.375922203063965, 2.7154557704925537, 1.9393302202224731, 2.037332057952881, 2.3895223140716553, 1.242501139640808, 2.203519821166992, 3.2104320526123047, 2.4208078384399414, 2.2449846267700195, 1.5751579999923706, 1.8146038055419922, 3.0609307289123535, 1.1018810272216797, 2.024287223815918, 3.2404472827911377, 2.5403850078582764, 2.0678398609161377, 2.0315818786621094, 1.844651699066162, 3.0741641521453857, 1.772470474243164, 1.786266565322876, 2.069413185119629, 1.5843209028244019, 1.1426420211791992, 2.0271196365356445, 1.5011217594146729, 1.8197966814041138, 2.1821510791778564, 2.7225940227508545, 2.753190279006958, 1.091414451599121, 1.2547180652618408, 2.4079442024230957, 3.0342986583709717, 1.1896637678146362, 2.5288572311401367, 1.5163582563400269, 1.3847455978393555, 1.629114031791687, 1.342976450920105, 1.8282499313354492, 3.8021132946014404, 2.4947328567504883, 1.451133131980896, 2.3916311264038086, 1.9960741996765137, 2.0364668369293213, 2.3313186168670654, 2.1169707775115967, 2.0903635025024414, 1.4593383073806763, 1.9136842489242554, 1.7450097799301147, 1.521895408630371, 2.49082350730896, 2.6054511070251465, 3.418471574783325, 1.2337367534637451, 1.277076005935669, 1.248437762260437, 1.4764543771743774, 1.714500904083252, 2.905543565750122, 3.04729962348938, 1.8532510995864868, 1.747176170349121, 2.159173011779785, 1.4303086996078491, 2.43021297454834, 1.585627555847168, 1.709848403930664, 2.307370185852051, 2.2816696166992188, 1.7129888534545898, 2.614129066467285, 1.7220077514648438, 1.7716155052185059, 1.060341715812683, 1.7905396223068237, 1.0155458450317383, 1.5323705673217773, 1.5771355628967285, 1.5401897430419922, 1.9908275604248047, 1.8701772689819336, 2.2133069038391113, 2.0276503562927246, 2.5726590156555176, 1.673762321472168, 3.1190521717071533, 1.7801650762557983, 2.298222541809082, 1.6821987628936768, 1.6645745038986206, 1.460677146911621, 2.2663888931274414, 2.51210618019104, 1.1576584577560425, 2.4569320678710938, 1.549902319908142, 1.8735283613204956, 2.1771326065063477, 0.8275594711303711, 2.1559627056121826, 1.1815497875213623, 2.0687074661254883, 2.2212343215942383, 2.2135276794433594, 1.8983737230300903, 1.9149116277694702, 1.6729192733764648, 1.5233432054519653, 1.4408187866210938, 1.3539434671401978, 2.857487916946411, 1.2362594604492188, 1.9771188497543335, 2.03279972076416, 1.4405486583709717, 2.2591638565063477, 2.0479955673217773, 2.4252471923828125, 1.5490217208862305, 1.6359939575195312, 1.977015495300293, 3.0593786239624023, 1.4737730026245117, 1.5938652753829956, 2.2951533794403076, 1.9287099838256836, 2.1671700477600098, 1.7584638595581055, 2.368070363998413, 1.9689054489135742, 0.6121898293495178, 1.8276790380477905, 1.9568884372711182, 2.469353199005127, 1.6363152265548706, 2.328765869140625, 1.8695975542068481, 1.3340418338775635, 1.3659621477127075, 1.8893003463745117, 2.4347996711730957, 1.7412115335464478, 2.485893726348877, 2.6001176834106445, 1.9338887929916382, 1.3884223699569702, 2.883349657058716, 1.150069236755371, 1.4014335870742798, 1.9209295511245728, 1.8633062839508057, 1.8696155548095703, 1.936511754989624, 2.684453010559082, 2.227922201156616, 2.7832674980163574, 1.9425731897354126, 2.122159004211426, 1.881480097770691, 1.884494423866272, 2.9421467781066895, 1.8206452131271362, 2.605196714401245, 1.1495765447616577, 2.591547727584839, 1.4387998580932617, 1.104872703552246, 1.741658329963684, 2.4353322982788086, 1.3947557210922241, 1.8344606161117554, 1.5784151554107666, 3.0376007556915283, 2.9991979598999023, 2.6726973056793213, 2.830322742462158, 1.6954561471939087, 2.5237019062042236, 2.479386329650879, 1.32725989818573, 3.3009724617004395, 1.431840181350708, 2.589190721511841, 1.771170735359192, 1.467900037765503, 3.041417121887207, 2.4758100509643555, 1.9815499782562256, 2.0468530654907227, 1.9833287000656128, 2.724713087081909, 1.4513516426086426, 1.4666290283203125, 2.665911912918091, 1.816092848777771, 1.7869516611099243, 1.7547158002853394, 2.150759696960449, 2.1679906845092773, 2.71126651763916, 0.7272443771362305, 1.2197407484054565, 1.8503320217132568, 2.8705642223358154, 1.6935890913009644, 1.78258216381073, 1.384785532951355, 2.689157724380493, 1.6375759840011597, 1.665261149406433, 1.2737778425216675, 3.161630392074585, 1.8888814449310303, 1.2239121198654175, 1.55555260181427, 1.3196648359298706, 2.686183452606201, 2.276944160461426, 1.4191619157791138, 2.202385902404785, 2.6846752166748047, 0.9854516386985779, 2.1274161338806152, 1.3815613985061646, 2.8341634273529053, 1.8459140062332153, 1.77967369556427, 1.566800832748413, 0.9514684677124023, 1.8681919574737549, 1.246614694595337, 2.271961212158203, 2.5528573989868164, 1.6175163984298706, 2.7137107849121094, 2.072751522064209, 2.4001054763793945, 1.0012599229812622, 1.8459657430648804, 2.152578115463257, 2.690479040145874, 2.1073455810546875, 2.3974883556365967, 1.7271838188171387, 0.8261518478393555, 1.8775444030761719, 1.7851316928863525, 2.0214478969573975, 2.3861348628997803, 1.45146644115448, 2.087942123413086, 2.221463203430176, 2.253782033920288, 2.531639575958252, 1.773676872253418, 1.6826238632202148, 1.6050728559494019, 2.3623528480529785, 1.7087777853012085, 0.8623167872428894, 1.7847211360931396, 1.2226626873016357, 1.5888770818710327, 2.5363738536834717, 0.02330421842634678, 0.028004556894302368, 0.05628468841314316, 0.03880536928772926, 0.1294516921043396, 0.09075362980365753, 0.05121403560042381, 0.0225700493901968, 0.017939208075404167, 0.06753529608249664, 0.1113230511546135, 0.06414992362260818, 0.059643201529979706, 0.04792700707912445, 0.0793551355600357, 0.054339248687028885, 1.1975168490607757e-05, 0.027270514518022537, 0.14472466707229614, 0.04046916961669922, 0.048417966812849045, 0.08781197667121887, 0.02492932230234146, 0.02150156907737255, 0.11844632774591446, 0.06947851181030273, 0.16156047582626343, 0.01103570219129324, 0.00265654013492167, 0.06302101165056229, 0.05430591478943825, 0.05437856540083885, 0.029551446437835693, 0.05733103305101395, 0.08172281831502914, 0.04413199424743652, 9.018182754516602e-05, 0.08528818190097809, 0.02789938449859619, 0.0028746365569531918, 0.07368992269039154, 0.026598390191793442, 0.0020892773754894733, 0.07675580680370331, 0.07080040127038956, 0.06228991970419884, 0.0878375768661499, 0.05081743001937866, 0.07558655738830566, 0.10824334621429443, 0.06251516193151474, 0.0758468508720398, 0.025532223284244537, 0.02346177026629448, 0.031468991190195084, 0.006822408176958561, 0.07578545808792114, 0.06780411303043365, 0.09926506876945496, 0.05483853816986084, 0.04823964089155197, 0.0759330466389656, 0.05449462682008743, 0.04673360660672188, 0.05324617400765419, 0.06757132709026337, 0.035024940967559814, 0.10054683685302734, 0.0046724616549909115, 0.05646491050720215, 0.12453469634056091, 0.06792747974395752, 0.06324446201324463, 0.012399313040077686, 0.09913301467895508, 0.011570131406188011, 0.014872470870614052, 0.04966044798493385, 0.07497460395097733, 0.06020038574934006, 0.03374429792165756, 0.10151167958974838, 0.09437204897403717, 0.01982070319354534, 0.09732726961374283, 0.05913009122014046, 0.05479593202471733, 0.04034103453159332, 0.04514965042471886, 0.07819674164056778, 0.026478495448827744, 0.07711918652057648, 0.07357683777809143, 0.04232661798596382, 0.058659572154283524, 0.07153451442718506, 0.09371452033519745, 0.032865047454833984, 0.009850924834609032, 0.050843190401792526, 0.045361220836639404, 0.11125872284173965, 0.09662037342786789, 0.11983480304479599, 0.06178926303982735, 0.025769108906388283, 0.004667580593377352, 0.006562549155205488, 0.08339990675449371, 0.11599041521549225, 0.08363208919763565, 0.022391008213162422, 0.05852346122264862, 0.09743943065404892, 0.05538639798760414, 0.03399413824081421, 0.06042541190981865, 0.0008235007408075035, 0.10415267944335938, 0.05140749737620354, 0.156411275267601, 0.07152575254440308, 0.06712859869003296, 0.0, 0.03313060849905014, 0.10258658975362778, 0.03725626319646835, 0.08375607430934906, 0.1363362967967987, 0.06010317802429199, 0.1167941465973854, 0.07187490165233612, 0.05854276567697525, 0.06969285011291504, 0.0487855039536953, 0.08787798881530762, 0.09698106348514557, 0.03426745533943176, 0.06542050093412399, 0.08176374435424805, 0.13683104515075684, 0.10194545239210129, 0.045955151319503784, 0.021403875201940536, 0.004177683498710394, 0.0807422399520874, 0.03885015472769737, 0.06127357482910156, 0.09687551110982895, 0.09022921323776245, 0.0736352726817131, 0.021910429000854492, 0.05994558334350586, 0.13040319085121155, 0.10040807723999023, 0.04671679437160492, 0.07515382766723633, 0.07278601825237274, 0.01087760180234909, 0.05016469955444336, 0.05231018364429474, 0.03964883089065552, 0.06957650184631348, 0.023101521655917168, 0.07836617529392242, 0.0506737157702446, 0.06041118875145912, 0.04130266606807709, 0.07811222970485687, 0.0661512091755867, 0.09601044654846191, 0.1377010941505432, 0.0479804202914238, 0.07632365822792053, 0.14179769158363342, 0.09147763252258301, 0.1332228183746338, 0.10077515244483948, 0.05246754363179207, 0.06332826614379883, 0.06660949438810349, 0.09911419451236725, 0.14989392459392548, 0.06043911725282669, 0.05666038393974304, 0.03597967326641083, 0.022164281457662582, 0.07541162520647049, 0.0803636759519577, 0.07496830075979233, 0.088716521859169, 0.10326988995075226, 0.05744459852576256, 0.07548204064369202, 0.08171551674604416, 0.07859653979539871, 0.09482993930578232, 0.07217993587255478, 0.11466091871261597, 0.10768329352140427, 0.032460425049066544, 0.04400614649057388, 0.08732040226459503, 0.08510531485080719, 0.07224608957767487, 0.08109661191701889, 0.09091435372829437, 0.038072679191827774, 0.06121329590678215, 0.1043730303645134, 0.03195023909211159, 0.05081396922469139, 0.0452822707593441, 0.10911251604557037, 0.059958409518003464, 0.030475065112113953, 0.038387563079595566, 0.08820729702711105, 0.05275392532348633, 0.05984153598546982, 0.050281867384910583, 0.15578210353851318, 0.05198155343532562, 0.0034907637163996696, 0.04673516005277634, 0.12427989393472672, 0.05989044904708862, 0.11849772930145264, 0.03344322741031647, 0.06462973356246948, 0.061517924070358276, 0.031590282917022705, 0.12533925473690033, 0.06230372190475464, 0.12632447481155396, 0.07859078049659729, 0.08850032836198807, 0.04229847714304924, 0.07262402027845383, 0.1462530493736267, 0.018727533519268036, 0.010834285989403725, 0.08633977919816971, 0.08816903084516525, 0.06480759382247925, 0.07249775528907776, 0.1206897497177124, 0.13377554714679718, 0.12032842636108398, 0.059492241591215134, 0.07182114571332932, 0.03184085711836815, 0.02821258455514908, 0.0975191593170166, 0.046063508838415146, 0.1395917683839798, 0.07053893804550171, 0.08617187291383743, 0.06442665308713913, 0.03420746326446533, 0.11962097883224487, 0.04805588722229004, 0.09505108743906021, 0.06708139926195145, 0.0664602518081665, 0.08233575522899628, 0.031683214008808136, 0.09457254409790039, 0.04390496015548706, 0.03736918419599533, 0.06401985883712769, 0.13025371730327606, 0.057454608380794525, 0.0278805959969759, 0.0547650009393692, 0.05620633065700531, 0.054653484374284744, 0.059654176235198975, 0.09969218820333481, 0.08931563049554825, 0.09238441288471222, 0.0392192117869854, 0.03237518295645714, 0.05898384749889374, 0.025764478370547295, 0.02765246108174324, 0.059442128986120224, 0.03646746650338173, 0.059139735996723175, 0.1021304652094841, 0.06963033974170685, 0.05884910374879837, 0.10834085196256638, 0.13123923540115356, 0.11315976828336716, 0.07509718090295792, 0.02783740498125553, 0.03133782744407654, 0.06832335144281387, 0.06709397584199905, 0.21622143685817719, 0.47622451186180115, 0.5483434200286865, 0.44729650020599365, 0.3862389028072357, 0.3015611469745636, 0.7007967233657837, 0.8133236765861511, 0.44238272309303284, 0.610508382320404, 0.40841227769851685, 0.3592115342617035, 0.4639970362186432, 0.4058413505554199, 0.4851725697517395, 0.5376610159873962, 0.3567047119140625, 0.7690356373786926, 0.3454844355583191, 0.4044734537601471, 0.4353151321411133, 0.48356372117996216, 0.5388154983520508, 0.38544028997421265, 0.42205360531806946, 0.07718107849359512, 0.3700653612613678, 0.17525483667850494, 0.42138609290122986, 0.6307202577590942, 0.3960563838481903, 0.2867504358291626, 0.3820757269859314, 0.38699716329574585, 0.3345246911048889, 0.3207535445690155, 0.413064181804657, 0.5187125205993652, 0.294760525226593, 0.48106488585472107, 0.4973747432231903, 0.8478652834892273, 0.26779651641845703, 0.18637870252132416, 0.6197546720504761, 0.6856689453125, 0.30169785022735596, 0.16247275471687317, 0.5007486343383789, 0.3501196503639221, 0.36672186851501465, 0.3491489291191101, 0.5879015326499939, 0.26503071188926697, 0.44111913442611694, 0.5985457301139832, 0.20954051613807678, 0.7757536172866821, 0.9093853831291199, 0.1774461716413498, 0.4452333450317383, 0.09986221045255661, 0.4462592601776123, 0.7177851796150208, 0.3219672441482544, 0.25987255573272705, 0.08010917156934738, 0.4363780915737152, 0.6515868902206421, 0.4900240898132324, 0.41537585854530334, 0.34605517983436584, 0.17856772243976593, 0.3231055438518524, 0.5785174369812012, 0.44000887870788574, 0.2279982715845108, 0.2981533110141754, 0.5611118078231812, 0.6618465185165405, 0.7539112567901611, 0.3735276758670807, 0.21875599026679993, 0.265522301197052, 0.36566734313964844, 0.4458753168582916, 0.6847234964370728, 0.507740318775177, 0.6287482976913452, 0.3896104395389557, 0.320646196603775, 0.467567503452301, 0.24524644017219543, 0.3011239469051361, 0.3603075444698334, 0.45786604285240173, 0.41639944911003113, 0.5529666543006897, 0.5023881196975708, 0.21798396110534668, 0.2620044946670532, 0.6101704835891724, 0.8053649067878723, 0.18655745685100555, 0.610339879989624, 0.6783626675605774, 0.555814802646637, 0.48415717482566833, 0.27812671661376953, 0.22541314363479614, 0.3663025498390198, 0.5740740299224854, 0.4134191870689392, 0.5564224720001221, 0.26351016759872437, 0.5461118817329407, 0.3105728030204773, 0.36445116996765137, 0.33553558588027954, 0.8795211315155029, 0.2571256160736084, 0.4738069176673889, 0.454562246799469, 0.3208487629890442, 0.5343703627586365, 0.3222108483314514, 0.4254054129123688, 0.31775832176208496, 0.45233482122421265, 0.6152663826942444, 0.3739301860332489, 0.5564029216766357, 0.2024025171995163, 0.5632979869842529, 0.47564154863357544, 0.39396563172340393, 0.27899372577667236, 0.20138999819755554, 0.5137234330177307, 0.2861103415489197, 0.43745046854019165, 0.25617995858192444, 0.6314032077789307, 0.5768895745277405, 0.7353273630142212, 0.6259206533432007, 0.5310952067375183, 0.30682680010795593, 0.45789629220962524, 0.5973501205444336, 0.3960530757904053, 0.2027013748884201, 0.28124457597732544, 0.3020384907722473, 0.4785844385623932, 0.7579119801521301, 0.1321265548467636, 0.5290296673774719, 0.34394407272338867, 0.30986738204956055, 0.5455009937286377, 0.24892382323741913, 0.5300106406211853, 0.6333974599838257, 0.47490447759628296, 0.2519460618495941, 0.18339626491069794, 0.5769884586334229, 0.13210371136665344, 0.2753966748714447, 0.5917329788208008, 0.48538848757743835, 0.10232415795326233, 0.32538366317749023, 0.4378944933414459, 0.12322879582643509, 0.34342390298843384, 0.7074809074401855, 0.5601162910461426, 0.45245376229286194, 0.583728551864624, 0.5079035758972168, 0.5561080574989319, 0.8406955599784851, 0.2503657042980194, 0.4268561899662018, 0.3581741750240326, 0.2485598772764206, 0.38536399602890015, 0.3070957362651825, 0.4350832402706146, 0.5169999599456787, 0.6925714612007141, 0.5419129133224487, 0.4303019642829895, 0.3315550982952118, 0.3908213973045349, 0.4360390305519104, 0.350009948015213, 0.34677258133888245, 0.3879995346069336, 0.2922731041908264, 0.41748037934303284, 0.4435137212276459, 0.6902979612350464, 0.16444909572601318, 0.35569316148757935, 0.546127438545227, 0.6944185495376587, 0.5448236465454102, 0.43000364303588867, 0.31053903698921204, 0.2924962639808655, 0.3460588753223419, 0.6266836524009705, 0.43078741431236267, 0.4240003228187561, 0.441864550113678, 0.33276885747909546, 0.234267920255661, 0.32542580366134644, 0.39125141501426697, 0.33141106367111206, 0.5369702577590942, 0.5343433022499084, 0.6708915829658508, 0.4743300974369049, 0.47115570306777954, 0.8225992918014526, 0.3208145797252655, 0.30474504828453064, 0.5779765248298645, 0.34286239743232727, 0.49820831418037415, 0.45840469002723694, 0.5021600723266602, 0.19984179735183716, 0.30220815539360046, 0.6225337982177734, 0.417544424533844, 0.1978617012500763, 0.5541889667510986, 0.5737571120262146, 0.5730236768722534, 0.2748066186904907, 0.3116529881954193, 0.31278738379478455, 0.27584001421928406, 0.07295475155115128, 0.2048090696334839, 0.21320001780986786, 0.6170457601547241, 0.35157424211502075, 0.3226900100708008, 0.18388409912586212, 0.36121830344200134, 0.3052814304828644, 0.2671753764152527, 0.4698728024959564, 0.35161715745925903, 0.47013410925865173, 0.14274558424949646, 0.274141788482666, 0.27357757091522217, 0.2256280779838562, 0.3376378118991852, 0.508933424949646, 0.43265655636787415, 0.31171587109565735, 0.3774224817752838, 0.21909955143928528, 0.30261892080307007, 0.19952018558979034, 0.24990057945251465, 0.4610864222049713, 0.554185152053833, 0.8105499148368835, 0.5603770613670349, 0.3677789270877838, 0.4360577166080475, 0.3167422115802765, 0.5531102418899536, 0.3171466290950775, 0.3629549443721771, 0.6394518613815308, 0.5955849885940552, 0.3529589772224426, 0.2702733874320984, 0.559166431427002, 0.377999484539032, 0.20070324838161469, 0.6924999952316284, 0.3615168035030365, 0.5879909992218018, 0.6339784264564514, 0.6554432511329651, 0.3125397562980652, 0.2281421273946762, 0.4151732921600342, 0.46266210079193115, 10.000045776367188, 26.894210815429688, 46.72269058227539, 35.07117462158203, 43.0397834777832, 42.66495132446289, 51.497283935546875, 10.590423583984375, 105.0106201171875, 32.87648010253906, 10.407736778259277, 41.3726692199707, 23.652877807617188, 7.1554412841796875, 15.886363983154297, 52.74169921875, 24.973867416381836, 40.19702911376953, 10.131871223449707, 16.205158233642578, 42.906944274902344, 10.004849433898926, 57.89276123046875, 13.295306205749512, 12.855682373046875, 11.480472564697266, 26.314350128173828, 26.63580322265625, 47.878143310546875, 49.53518295288086, 16.333236694335938, 70.35516357421875, 26.685546875, 36.58840560913086, 34.0657958984375, 13.08568286895752, 72.42108154296875, 9.678716659545898, 21.512069702148438, 13.298566818237305, 22.128612518310547, 14.789810180664062, 30.07376480102539, 34.01849365234375, 31.94491195678711, 27.78175926208496, 56.22638702392578, 11.334120750427246, 26.788818359375, 74.54012298583984, 18.59161376953125, 54.22024154663086, 19.21552848815918, 40.86768341064453, 12.92059326171875, 54.48358154296875, 27.066347122192383, 34.28938293457031, 17.58776092529297, 66.03251647949219, 33.7718505859375, 86.55489349365234, 31.73728370666504, 27.066917419433594, 27.40787124633789, 22.705751419067383, 31.792118072509766, 25.849760055541992, 32.657352447509766, 123.2595443725586, 22.35882568359375, 39.17702865600586, 24.521257400512695, 52.17742919921875, 8.439032554626465, 22.730619430541992, 40.54859161376953, 52.956111907958984, 35.80790710449219, 43.22227478027344, 8.591279983520508, 13.391066551208496, 16.867897033691406, 40.76495361328125, 48.729339599609375, 13.230804443359375, 51.25810241699219, 47.11308670043945, 27.72525405883789, 28.95673942565918, 33.08709716796875, 29.627914428710938, 50.145263671875, 52.96120834350586, 17.813772201538086, 47.77907943725586, 31.98182487487793, 25.91232681274414, 13.57659912109375, 24.10529899597168, 26.35474967956543, 21.676250457763672, 39.94636535644531, 14.52867317199707, 31.01429557800293, 18.899513244628906, 13.453338623046875, 59.61489486694336, 18.435138702392578, 20.513797760009766, 10.478363037109375, 41.32249450683594, 49.54267501831055, 48.97425079345703, 36.87493896484375, 15.290534019470215, 22.572338104248047, 20.312175750732422, 39.15582275390625, 72.18174743652344, 54.77901077270508, 25.80964469909668, 17.956314086914062, 27.84101676940918, 25.143949508666992, 18.248321533203125, 56.827205657958984, 21.12809944152832, 65.26781463623047, 16.551332473754883, 14.149137496948242, 18.834135055541992, 22.077919006347656, 53.180755615234375, 25.120956420898438, 16.749065399169922, 19.51348114013672, 13.436037063598633, 63.2791748046875, 27.904701232910156, 56.49371337890625, 17.453006744384766, 23.979949951171875, 41.602508544921875, 27.8382511138916, 21.1710205078125, 31.3377685546875, 10.44057559967041, 54.7852783203125, 34.853336334228516, 71.33334350585938, 35.08340072631836, 57.52336883544922, 55.4142951965332, 18.31923484802246, 56.73504638671875, 26.94902801513672, 39.40437316894531, 34.72297668457031, 34.8038330078125, 21.84036636352539, 12.50815486907959, 56.266204833984375, 25.363040924072266, 94.03778076171875, 30.081512451171875, 18.128753662109375, 21.07099723815918, 21.426605224609375, 39.325164794921875, 26.33782958984375, 56.898475646972656, 16.97431755065918, 23.450668334960938, 42.68370056152344, 17.0264892578125, 52.45947265625, 14.342559814453125, 31.054460525512695, 18.93739128112793, 44.536834716796875, 10.722975730895996, 16.343017578125, 20.5071964263916, 12.118278503417969, 15.686043739318848, 9.407038688659668, 36.37493896484375, 29.203880310058594, 49.4577522277832, 23.889310836791992, 36.33648681640625, 34.84588623046875, 62.29384994506836, 30.06134033203125, 16.754392623901367, 27.169525146484375, 110.27909088134766, 14.875136375427246, 18.393798828125, 25.7780704498291, 12.2012939453125, 13.67747974395752, 17.12769889831543, 29.29124641418457, 67.35262298583984, 28.29017448425293, 37.47813415527344, 43.116859436035156, 9.04723834991455, 105.54464721679688, 18.51663589477539, 12.132965087890625, 49.09737777709961, 147.25146484375, 32.187408447265625, 13.5654878616333, 21.87434196472168, 45.2808837890625, 25.691864013671875, 41.35698318481445, 34.63969421386719, 27.721988677978516, 33.88762664794922, 31.44499969482422, 24.919584274291992, 36.148773193359375, 48.946258544921875, 28.721317291259766, 12.31195068359375, 32.072479248046875, 57.423309326171875, 70.32057189941406, 25.08394432067871, 22.511959075927734, 32.3807258605957, 36.85535430908203, 12.097383499145508, 40.1260986328125, 52.4847412109375, 79.67041015625, 10.746508598327637, 75.96465301513672, 70.0673828125, 69.55758666992188, 44.10602569580078, 25.23441505432129, 42.403900146484375, 19.96750259399414, 29.8201904296875, 15.200470924377441, 15.746612548828125, 10.34185791015625, 22.158926010131836, 43.31471633911133, 42.198577880859375, 19.427886962890625, 30.271982192993164, 22.591415405273438, 78.13284301757812, 18.11639404296875, 9.859634399414062, 69.49114990234375, 27.1494140625, 9.197991371154785, 65.89701843261719, 27.74820327758789, 20.778182983398438, 39.99477767944336, 18.62542724609375, 15.381103515625, 25.393423080444336, 36.36381912231445, 28.389101028442383, 56.56826400756836, 18.3675537109375, 8.819793701171875, 57.360740661621094, 29.473134994506836, 70.44091033935547, 39.63217544555664, 6.306060791015625, 29.0814208984375, 31.759023666381836, 32.56004333496094, 44.023353576660156, 12.31595230102539, 17.689361572265625, 51.30126953125, 24.67364501953125, 18.307024002075195, 21.64471435546875, 35.841796875, 31.159452438354492, 53.917015075683594, 15.475021362304688, 39.963592529296875, 76.29356384277344, 20.662504196166992, 21.06422233581543, 1.8010222911834717, 1.704559087753296, 1.5205285549163818, 2.3198578357696533, 1.9722009897232056, 1.746682047843933, 2.2369437217712402, 2.527052164077759, 3.4758293628692627, 1.6175838708877563, 2.1714305877685547, 1.8319355249404907, 2.7149345874786377, 1.287378191947937, 2.082848072052002, 1.8119820356369019, 1.487831950187683, 2.031805992126465, 2.1887388229370117, 1.5648107528686523, 1.9002732038497925, 1.883540153503418, 3.255937337875366, 2.5179431438446045, 2.358612060546875, 2.204366445541382, 2.4473891258239746, 1.6352776288986206, 2.3926048278808594, 2.204026222229004, 2.4084596633911133, 2.6104326248168945, 2.804741382598877, 2.7388627529144287, 1.2268785238265991, 1.9484752416610718, 2.2030718326568604, 1.2264660596847534, 2.196206569671631, 1.356160044670105, 1.7542781829833984, 1.6771706342697144, 1.985915184020996, 1.8155149221420288, 2.1336452960968018, 2.272721290588379, 3.177804470062256, 2.764503002166748, 1.1275155544281006, 2.398404359817505, 2.0020699501037598, 2.6857988834381104, 1.5593950748443604, 1.7826604843139648, 1.9401664733886719, 1.7018988132476807, 1.482600212097168, 2.3183300495147705, 1.9036072492599487, 2.194563627243042, 3.1308794021606445, 1.7295305728912354, 2.526638984680176, 2.4173293113708496, 1.8232550621032715, 0.8973737955093384, 2.391655921936035, 1.7279562950134277, 2.669389009475708, 1.6294240951538086, 2.3038766384124756, 1.383919596672058, 1.37311851978302, 2.385178804397583, 3.0147368907928467, 2.1980412006378174, 2.202763557434082, 3.1123461723327637, 2.419562339782715, 1.7546491622924805, 2.7061831951141357, 2.871392250061035, 1.311488151550293, 2.2271852493286133, 2.0582385063171387, 1.843047857284546, 2.5416903495788574, 2.395796775817871, 2.151545524597168, 1.7214269638061523, 1.121779441833496, 2.0805983543395996, 1.7082700729370117, 3.288814067840576, 1.299676775932312, 1.351069450378418, 1.721026062965393, 2.084251880645752, 2.011164665222168, 1.8152439594268799, 1.359475016593933, 2.06734299659729, 2.6402642726898193, 1.582324504852295, 1.1580114364624023, 2.023144483566284, 0.10421107709407806, 2.9425506591796875, 3.506812334060669, 2.144489288330078, 2.54536771774292, 2.0897741317749023, 2.717211961746216, 1.8229416608810425, 2.692535400390625, 2.376532554626465, 1.6563200950622559, 1.8707809448242188, 1.4340651035308838, 2.412012815475464, 2.1120412349700928, 2.1897428035736084, 2.0296404361724854, 2.4090373516082764, 2.4190914630889893, 2.003065824508667, 2.02543568611145, 2.4040706157684326, 2.3490262031555176, 2.143359422683716, 2.1840410232543945, 2.211209297180176, 2.8866260051727295, 1.4556268453598022, 2.3918681144714355, 1.1134613752365112, 1.1425411701202393, 1.7582893371582031, 1.8608118295669556, 2.3992793560028076, 2.677088975906372, 1.7695165872573853, 2.4671993255615234, 1.959650993347168, 2.45418643951416, 2.8285393714904785, 1.7598981857299805, 2.626436948776245, 2.255476951599121, 1.8802754878997803, 1.5193344354629517, 2.4915335178375244, 1.3703079223632812, 1.8288484811782837, 1.8760203123092651, 1.6712660789489746, 2.263363838195801, 1.24638831615448, 1.4170773029327393, 2.1855154037475586, 2.0184357166290283, 0.7712926864624023, 1.3280935287475586, 1.580342173576355, 2.394974946975708, 2.533830165863037, 2.323288917541504, 1.5054901838302612, 1.033095359802246, 1.427693247795105, 3.2335221767425537, 3.0100529193878174, 2.867368698120117, 0.9273293614387512, 2.2628164291381836, 1.71996009349823, 1.8706895112991333, 2.988713264465332, 1.5258138179779053, 1.2392128705978394, 1.5133590698242188, 1.3537479639053345, 1.44688880443573, 1.80332350730896, 3.018447160720825, 2.1364357471466064, 1.685158610343933, 2.2324001789093018, 2.6887435913085938, 1.4677495956420898, 1.9173040390014648, 2.38887882232666, 1.5387645959854126, 1.4887773990631104, 1.1570953130722046, 1.5802721977233887, 1.7832642793655396, 1.7668981552124023, 2.49992299079895, 2.086277961730957, 1.3545159101486206, 3.089007616043091, 2.6567704677581787, 1.8232436180114746, 2.1377060413360596, 1.5895763635635376, 2.277062177658081, 2.1527798175811768, 1.3278074264526367, 1.3453741073608398, 1.370326042175293, 2.1007041931152344, 1.7430559396743774, 2.724719285964966, 1.260472297668457, 2.2377209663391113, 1.2804518938064575, 1.985800862312317, 1.4665603637695312, 2.125027656555176, 1.8856545686721802, 2.596724271774292, 2.088301420211792, 1.9645720720291138, 1.9280462265014648, 1.1937824487686157, 3.144090414047241, 1.5221613645553589, 2.4328813552856445, 2.7934811115264893, 2.6892662048339844, 1.4799091815948486, 2.3454620838165283, 2.22805118560791, 2.1397671699523926, 2.8144969940185547, 2.296921730041504, 1.8959767818450928, 1.2163974046707153, 1.4387482404708862, 1.9232375621795654, 1.8705111742019653, 1.6267385482788086, 1.323628544807434, 2.0599756240844727, 3.1081531047821045, 2.0784361362457275, 2.2944040298461914, 3.030395984649658, 2.180342674255371, 2.5433952808380127, 1.9394619464874268, 2.732306480407715, 1.504469871520996, 3.0241198539733887, 2.925065279006958, 1.7846311330795288, 1.6757515668869019, 2.530527353286743, 1.3563889265060425, 1.781197428703308, 2.525209903717041, 1.9696264266967773, 1.8488569259643555, 1.4650062322616577, 1.240315318107605, 1.493483543395996, 2.0349645614624023, 3.1704728603363037, 2.479296922683716, 1.573328971862793, 3.3000402450561523, 3.1350109577178955, 1.9251221418380737, 2.9517104625701904, 2.3720757961273193, 2.6410491466522217, 1.942362904548645, 2.406327247619629, 2.05460786819458, 1.9535202980041504, 1.8371977806091309, 1.5642304420471191, 1.1297664642333984, 2.6104815006256104, 1.750899314880371, 1.8384695053100586, 2.336247444152832, 1.6216650009155273, 2.2877614498138428, 1.6495146751403809, 2.4849658012390137, 0.8720216155052185, 2.089442491531372, 2.0916812419891357, 2.415231943130493, 2.946971893310547, 1.6847455501556396, 0.9694995880126953, 2.434859275817871, 0.04868769645690918, 0.0729900375008583, 0.05553930997848511, 0.069200798869133, 0.030810296535491943, 0.029711060225963593, 0.08893280476331711, 0.05513273552060127, 0.04822564870119095, 0.07471055537462234, 0.14236946403980255, 0.14810612797737122, 0.03947724401950836, 0.07078003883361816, 0.025988277047872543, 0.08020991086959839, 0.05316850543022156, 0.07783012837171555, 0.019983887672424316, 0.04820011928677559, 0.10729631781578064, 0.028461432084441185, 0.06530576944351196, 0.08833916485309601, 0.019531715661287308, 0.053820934146642685, 0.10124480724334717, 0.05918759107589722, 0.05277729779481888, 0.05986011028289795, 0.03850638493895531, 0.03936517983675003, 0.036151349544525146, 0.004662730731070042, 0.11167490482330322, 0.05404634401202202, 0.06742849946022034, 0.0585600845515728, 0.0772329568862915, 0.10050800442695618, 0.06654823571443558, 0.08446439355611801, 0.07849917560815811, 0.04029645025730133, 0.13955210149288177, 0.11225736141204834, 0.09758210927248001, 0.11112720519304276, 0.09737297147512436, 0.06040589138865471, 0.08295880258083344, 0.08412672579288483, 0.07204363495111465, 0.05726039782166481, 0.05391502380371094, 0.11580520123243332, 0.017684830352663994, 0.010811476036906242, 0.11023914068937302, 0.05754154920578003, 0.03719181939959526, 0.04622138291597366, 0.03563624247908592, 0.06850355118513107, 0.014884162694215775, 0.0776895061135292, 0.08671495318412781, 0.07013148069381714, 0.05179053172469139, 0.013889498077332973, 0.15393877029418945, 0.014223160222172737, 0.10508771985769272, 0.04699823260307312, 0.07786362618207932, 0.09064004570245743, 0.0693911537528038, 0.043970320373773575, 0.10920167714357376, 0.0694049596786499, 0.06133866310119629, 0.07406437397003174, 0.030348455533385277, 0.048270080238580704, 0.0, 0.04716978967189789, 0.08728170394897461, 0.09757877141237259, 0.1621168851852417, 0.00169123406521976, 0.04360199719667435, 0.09804405272006989, 0.06785315275192261, 0.06257183104753494, 0.06778912991285324, 0.08986902236938477, 0.06478559970855713, 0.0453675352036953, 0.11254911869764328, 0.09728862345218658, 0.020880430936813354, 0.07759780436754227, 0.08895517140626907, 0.06728411465883255, 0.13043677806854248, 0.011179668828845024, 0.038788020610809326, 0.06599199771881104, 0.022298306226730347, 0.1483047604560852, 0.08615010976791382, 0.08413716405630112, 0.0584372840821743, 0.13707998394966125, 0.04797792434692383, 0.09304660558700562, 0.09520792961120605, 0.10529177635908127, 0.09172306209802628, 0.11781051009893417, 0.14167985320091248, 0.1254536509513855, 0.043259505182504654, 0.033421821892261505, 0.1105617880821228, 0.045565247535705566, 0.021910429000854492, 0.08763253688812256, 0.028369545936584473, 0.03459550067782402, 0.10098852217197418, 0.022141000255942345, 0.12243153154850006, 0.02338045835494995, 0.06195920705795288, 0.08482593297958374, 0.09438452869653702, 0.062002990394830704, 0.07864350080490112, 0.10454392433166504, 0.004140995442867279, 0.10448282212018967, 0.0694623813033104, 0.07839570194482803, 0.034896980971097946, 0.053428053855895996, 0.08151890337467194, 0.12360429763793945, 0.08384976536035538, 0.057991139590740204, 0.05897965654730797, 0.011897658929228783, 0.029482586309313774, 0.022937536239624023, 0.03832412138581276, 0.05032135918736458, 0.0847313404083252, 0.14468030631542206, 0.07490342855453491, 0.04513335973024368, 0.04944673553109169, 0.07605856657028198, 0.019550524652004242, 0.07750120759010315, 0.04273802042007446, 0.05977630615234375, 0.024901241064071655, 0.05255557969212532, 0.06161727383732796, 0.062479257583618164, 0.13206467032432556, 0.05416865274310112, 0.0887441635131836, 0.03133755922317505, 0.150430366396904, 0.07845532149076462, 0.09345995634794235, 0.048891838639974594, 0.07185264676809311, 0.09588535130023956, 0.037581026554107666, 0.053396012634038925, 0.0968329906463623, 0.06165009364485741, 0.0827426165342331, 0.006128971930593252, 0.11421585083007812, 0.04028172418475151, 0.1158641055226326, 0.1157606840133667, 0.06032897159457207, 0.1000727117061615, 0.03348866477608681, 0.07249557971954346, 0.023598110303282738, 0.07696032524108887, 0.0868084505200386, 0.035522572696208954, 0.024426529183983803, 0.031717486679553986, 0.037313204258680344, 0.09593957662582397, 0.09053642302751541, 0.021571414545178413, 0.033334970474243164, 0.1541016697883606, 0.09010441601276398, 0.07775598019361496, 0.08350341767072678, 0.03255583718419075, 0.09052080661058426, 0.06499195843935013, 0.084492526948452, 0.07593511790037155, 0.0008989613852463663, 0.0483391135931015, 0.0, 0.06300783902406693, 0.10820566117763519, 0.06714683771133423, 0.06757397204637527, 0.057752836495637894, 0.09911399334669113, 0.038817889988422394, 0.09803193807601929, 0.08120494335889816, 0.0725136250257492, 0.05049850046634674, 0.019667088985443115, 0.10590362548828125, 0.051878973841667175, 0.06460052728652954, 0.13230711221694946, 0.08954807370901108, 0.1836910992860794, 0.06292099505662918, 0.08737323433160782, 0.03272818401455879, 0.08174359798431396, 0.03360467404127121, 0.05077745392918587, 0.05459630489349365, 0.12012356519699097, 0.05228471755981445, 0.09379436075687408, 0.056926168501377106, 0.05898767337203026, 0.12376533448696136, 0.012768545188009739, 0.15557557344436646, 0.0967441126704216, 0.036173172295093536, 0.03339850902557373, 0.06337644904851913, 0.05497531220316887, 0.05685951188206673, 0.07938962429761887, 0.05760423466563225, 0.08834966272115707, 0.07852089405059814, 0.09122580289840698, 0.04295998066663742, 0.11878402531147003, 0.0455792136490345, 0.058827418833971024, 0.06945037096738815, 0.10945849865674973, 0.02224564552307129, 0.10986363887786865, 0.06630200147628784, 0.08043234050273895, 0.1296156644821167, 0.07216645032167435, 0.0, 0.08501636236906052, 0.07596422731876373, 0.0555424690246582, 0.014063903130590916, 0.024012455716729164, 0.03794515132904053, 0.05375208705663681, 0.04984565079212189, 0.02289128303527832, 0.08493141829967499, 0.07119454443454742, 0.10742378979921341, 0.04562026262283325, 0.07556276768445969, 0.036859069019556046, 0.08360873907804489, 0.027537845075130463, 0.1287626475095749, 0.08013508468866348, 0.07850903272628784, 0.027543187141418457, 0.05915660783648491, 0.030620012432336807, 0.08064713329076767, 0.12727080285549164, 0.05204761028289795, 0.4078753590583801, 0.6968590617179871, 0.45848581194877625, 0.3524533808231354, 0.6874960064888, 0.4193894863128662, 0.45224326848983765, 0.4425002634525299, 0.22532503306865692, 0.8400126695632935, 0.3872329890727997, 0.3241126239299774, 0.5489400625228882, 0.40925613045692444, 0.10606851428747177, 0.5067993998527527, 0.44462496042251587, 0.46751928329467773, 0.38207125663757324, 0.7405813336372375, 0.4429772198200226, 0.5213046669960022, 0.9223775863647461, 0.3388436436653137, 0.30386078357696533, 0.32266661524772644, 0.314603716135025, 0.22081470489501953, 0.8101702928543091, 0.19168002903461456, 0.052910346537828445, 0.5029714107513428, 0.5848417282104492, 0.35493019223213196, 0.3787432312965393, 0.405396044254303, 0.41964179277420044, 0.24095241725444794, 0.9229278564453125, 0.6057669520378113, 0.8090254068374634, 0.45982328057289124, 0.3363533020019531, 0.214071586728096, 0.4412163197994232, 0.5228097438812256, 0.3863014280796051, 0.4148828089237213, 0.3462032973766327, 0.24269624054431915, 0.5973860025405884, 0.3415232300758362, 0.2558005452156067, 0.2576616108417511, 0.2832295894622803, 0.45141682028770447, 0.45283544063568115, 0.23623469471931458, 0.3588620722293854, 0.4926488399505615, 0.46657508611679077, 0.6365286111831665, 0.47447410225868225, 0.5991871356964111, 0.4169670641422272, 0.5961371660232544, 0.29804694652557373, 0.4209902882575989, 0.8998449444770813, 0.33419138193130493, 0.43152618408203125, 0.30007490515708923, 0.3281363546848297, 0.40463152527809143, 0.598141074180603, 0.4990755319595337, 0.44744551181793213, 0.11809646338224411, 0.6540089845657349, 0.49719515442848206, 0.21974903345108032, 0.7688072323799133, 0.5522246360778809, 0.6137694120407104, 0.5501663684844971, 0.788432776927948, 0.28203657269477844, 0.34582915902137756, 0.6497155427932739, 0.6040201783180237, 0.6338406801223755, 0.20694699883460999, 0.42443743348121643, 0.38566452264785767, 0.4606671929359436, 0.305061012506485, 0.22873763740062714, 0.4079211354255676, 0.259252667427063, 0.5125066041946411, 0.4798299968242645, 0.5172410607337952, 0.28737953305244446, 0.43834051489830017, 0.3191007971763611, 0.08167491853237152, 0.5568550229072571, 0.3788922131061554, 0.410358726978302, 0.5041276216506958, 0.2664060592651367, 0.36312055587768555, 0.25999271869659424, 0.4957253932952881, 0.35782095789909363, 0.5066829323768616, 0.25257182121276855, 0.42455145716667175, 0.17148299515247345, 0.42030012607574463, 0.3336153030395508, 0.4171088933944702, 0.8265528678894043, 0.44422897696495056, 0.7123738527297974, 0.19886676967144012, 0.35127273201942444, 0.4567022919654846, 0.5211983919143677, 0.978831946849823, 0.6490986347198486, 0.3062487244606018, 0.6758697628974915, 0.39848247170448303, 0.5593526363372803, 0.4902600347995758, 0.44314414262771606, 0.07957753539085388, 0.6956822276115417, 0.7550361752510071, 0.4899427592754364, 0.2860656678676605, 0.7511765360832214, 0.08614621311426163, 0.43925440311431885, 0.11032012850046158, 0.9253007173538208, 0.731573760509491, 0.5667439103126526, 0.49123266339302063, 0.49316859245300293, 0.42533984780311584, 0.5619592666625977, 0.6174045205116272, 0.6814907193183899, 0.40071502327919006, 0.4849407970905304, 0.6473040580749512, 0.6162892580032349, 0.24064575135707855, 0.41196227073669434, 0.320671945810318, 0.6384761333465576, 0.9888201951980591, 0.6474142074584961, 0.5617609620094299, 0.7362924814224243, 0.6731884479522705, 0.40596094727516174, 0.18287444114685059, 0.5602317452430725, 0.3554961681365967, 0.5471495985984802, 0.33085089921951294, 0.2983761429786682, 0.35358625650405884, 0.6462740898132324, 0.31507232785224915, 0.4309036433696747, 0.4448343813419342, 0.4865371286869049, 0.7015787959098816, 0.10157715529203415, 0.5028104186058044, 0.6089524030685425, 0.3190099895000458, 0.2537722885608673, 0.6912228465080261, 0.19544193148612976, 0.35894736647605896, 0.12204036116600037, 0.500770092010498, 0.6206973195075989, 0.5476425290107727, 0.1710730940103531, 0.4526548385620117, 0.3874334692955017, 0.3765174150466919, 0.9869548678398132, 0.4666058123111725, 0.6061267852783203, 0.36911407113075256, 0.27413421869277954, 0.557829737663269, 0.4862825572490692, 0.11524354666471481, 0.11693456023931503, 0.5982584953308105, 0.6968275308609009, 0.30940666794776917, 0.7310207486152649, 0.2579810917377472, 0.34782469272613525, 0.3477162718772888, 0.1699739247560501, 0.44071871042251587, 0.8128469586372375, 0.37246084213256836, 0.38204941153526306, 0.23501916229724884, 0.47851142287254333, 0.6540797352790833, 0.1999080628156662, 0.40440258383750916, 0.8142872452735901, 0.371947705745697, 0.305754154920578, 0.4434357285499573, 0.572165846824646, 0.18303735554218292, 0.5453130006790161, 0.6647434234619141, 0.6619569063186646, 0.4381507635116577, 0.6837044954299927, 0.25735199451446533, 0.5339664816856384, 0.2100353240966797, 0.6866143941879272, 0.20261363685131073, 0.8392010927200317, 0.4750213623046875, 0.6712313890457153, 0.5071741938591003, 0.5347297191619873, 0.4102703630924225, 0.3524806797504425, 0.9223210215568542, 0.439106285572052, 0.25264355540275574, 0.3366869390010834, 0.21958006918430328, 0.41574177145957947, 0.4037289321422577, 0.25458967685699463, 0.34023767709732056, 0.517893373966217, 0.162502720952034, 0.7814109921455383, 0.4160529673099518, 0.8301239013671875, 0.5585719347000122, 0.9311658143997192, 0.5251302123069763, 0.5490775108337402, 0.3200133442878723, 0.4507462978363037, 0.2475384920835495, 0.23963813483715057, 0.26570290327072144, 0.6032366752624512, 0.7255516052246094, 0.5249164700508118, 0.4852786958217621, 0.5116267800331116, 0.44706907868385315, 0.12654125690460205, 0.6575524806976318, 0.3294026851654053, 0.12550240755081177, 0.5033786296844482, 0.34407567977905273, 0.39635592699050903, 0.1858903467655182, 0.5142406821250916, 0.7465159296989441, 0.4227778911590576, 0.7718168497085571, 0.5927276611328125, 0.8458259105682373, 0.4128524959087372, 0.5095605850219727, 0.34974536299705505, 0.4800039529800415, 0.3672754466533661, 0.48599356412887573, 0.313972532749176, 0.2717444598674774, 0.5615498423576355, 0.09493686258792877, 7.085362434387207, 44.284759521484375, 12.205153465270996, 9.664764404296875, 53.91669845581055, 33.044677734375, 50.400482177734375, 31.047698974609375, 11.052764892578125, 9.74041748046875, 13.683197021484375, 30.441757202148438, 14.902689933776855, 11.576546669006348, 56.068641662597656, 39.49493408203125, 9.47283935546875, 20.490341186523438, 38.54873275756836, 17.558334350585938, 10.033599853515625, 47.58211898803711, 19.220367431640625, 19.57919692993164, 31.39935302734375, 12.998790740966797, 38.57780838012695, 43.386112213134766, 20.7868595123291, 33.08393096923828, 59.92349624633789, 18.482025146484375, 48.763641357421875, 37.79730224609375, 50.41463088989258, 61.90819549560547, 66.40399169921875, 11.043227195739746, 40.09937286376953, 19.79522705078125, 53.56089782714844, 11.60048770904541, 25.492467880249023, 98.5695571899414, 135.52255249023438, 22.221595764160156, 21.187591552734375, 17.624679565429688, 11.438201904296875, 9.858871459960938, 9.049774169921875, 42.198089599609375, 32.47845458984375, 21.52082061767578, 46.7191162109375, 47.98503494262695, 17.35053825378418, 52.07468795776367, 13.817156791687012, 19.12088394165039, 10.056564331054688, 41.03213119506836, 93.13442993164062, 38.70831298828125, 32.62785339355469, 60.6781005859375, 19.018163681030273, 14.372129440307617, 13.766845703125, 11.995943069458008, 16.452733993530273, 38.890907287597656, 28.41373062133789, 22.2823486328125, 16.667306900024414, 21.196578979492188, 26.50041389465332, 79.13339233398438, 36.71392822265625, 25.389482498168945, 19.966690063476562, 36.67498779296875, 29.32411003112793, 45.642822265625, 81.97325897216797, 47.02017593383789, 14.465911865234375, 11.030571937561035, 39.61997985839844, 9.980133056640625, 26.10224723815918, 36.721405029296875, 29.403045654296875, 69.6044692993164, 12.1937255859375, 49.356849670410156, 68.5958251953125, 23.72313690185547, 62.66831588745117, 19.022430419921875, 72.7532958984375, 39.81794738769531, 32.352989196777344, 28.949953079223633, 23.34268569946289, 20.26268196105957, 61.96820068359375, 10.05966854095459, 13.87786865234375, 112.70118713378906, 54.50551986694336, 50.71620178222656, 18.19996452331543, 22.86338996887207, 22.869047164916992, 16.548908233642578, 29.03056526184082, 33.6512336730957, 15.906700134277344, 89.94039154052734, 28.145980834960938, 39.33905029296875, 34.29473876953125, 20.92811393737793, 62.96808624267578, 19.030242919921875, 15.604689598083496, 48.98613357543945, 73.22113037109375, 54.837703704833984, 45.06103515625, 41.58444595336914, 34.87405014038086, 32.92388916015625, 17.915817260742188, 10.836029052734375, 89.49700927734375, 14.716796875, 30.151273727416992, 85.23040771484375, 27.3082275390625, 11.586959838867188, 37.99791717529297, 29.43446159362793, 41.55755615234375, 32.9122314453125, 113.91085815429688, 78.22054290771484, 58.8404541015625, 31.0205078125, 11.0003662109375, 33.16810607910156, 41.5317268371582, 29.13582420349121, 38.70623779296875, 28.40056610107422, 32.615962982177734, 35.34453201293945, 16.554122924804688, 54.77836608886719, 55.3133544921875, 119.97283935546875, 33.44707107543945, 67.84843444824219, 56.55341720581055, 52.69267272949219, 96.14076232910156, 34.25212478637695, 67.05432891845703, 35.276214599609375, 30.33854866027832, 10.67926025390625, 43.26212692260742, 12.233184814453125, 17.49591636657715, 76.64404296875, 10.75341796875, 41.7134895324707, 35.91431427001953, 22.5262451171875, 76.38346862792969, 33.28462600708008, 29.916654586791992, 65.19036865234375, 20.600976943969727, 39.781982421875, 24.59575653076172, 98.94054412841797, 28.110107421875, 34.39680480957031, 36.53041076660156, 62.43678665161133, 30.16279411315918, 28.144411087036133, 30.478588104248047, 71.63375854492188, 33.92083740234375, 53.651336669921875, 25.599227905273438, 21.8599853515625, 14.051422119140625, 50.35569381713867, 9.361517906188965, 33.06410217285156, 48.05167770385742, 29.914306640625, 17.01582145690918, 38.14324951171875, 20.95550537109375, 79.26028442382812, 9.327789306640625, 59.16603469848633, 13.162689208984375, 30.869647979736328, 35.63023376464844, 20.364837646484375, 26.442184448242188, 34.266937255859375, 39.42995834350586, 48.60731887817383, 63.9251708984375, 25.491641998291016, 60.31281661987305, 25.423553466796875, 50.982421875, 10.359365463256836, 46.637451171875, 16.922332763671875, 68.70758819580078, 25.63471221923828, 33.84292221069336, 12.180419921875, 83.68093872070312, 31.34609031677246, 65.61320495605469, 40.77851867675781, 37.534271240234375, 10.994294166564941, 34.078529357910156, 15.1551513671875, 51.069950103759766, 70.59673309326172, 40.026336669921875, 33.02830505371094, 15.633163452148438, 10.457282066345215, 89.567138671875, 31.077543258666992, 76.9044189453125, 31.089523315429688, 57.03993225097656, 18.538270950317383, 17.713829040527344, 13.207777976989746, 56.62282180786133, 26.11787223815918, 45.824188232421875, 17.359466552734375, 30.205976486206055, 12.341569900512695, 60.21983337402344, 25.00830078125, 25.4696044921875, 10.026336669921875, 8.080246925354004, 37.48141098022461, 15.845229148864746, 30.210174560546875, 10.529510498046875, 30.786865234375, 36.997283935546875, 13.435821533203125, 14.000595092773438, 29.20826530456543, 140.45433044433594, 35.53042221069336, 42.70566940307617, 31.59521484375, 14.073801040649414, 33.96363830566406, 21.53152847290039, 30.397430419921875, 29.114933013916016, 26.10823631286621, 19.152963638305664, 20.20654296875, 129.60720825195312, 29.83633041381836, 72.83670806884766, 39.86134338378906, 23.62359619140625, 57.51945114135742, 24.726444244384766, 14.984092712402344, 26.146820068359375, 14.408246994018555, 20.03302001953125, 14.871185302734375, 85.34329986572266, 21.53311538696289, 1.4460744857788086, 1.3414760828018188, 2.21079158782959, 1.3907138109207153, 1.8812284469604492, 1.8277267217636108, 3.0396840572357178, 1.4496737718582153, 2.587775230407715, 1.9583138227462769, 1.9805374145507812, 2.4563632011413574, 3.2698757648468018, 1.9665632247924805, 1.041474461555481, 2.993732213973999, 2.1198513507843018, 1.2307806015014648, 1.342806100845337, 1.6575477123260498, 1.8726013898849487, 1.2983906269073486, 2.263964891433716, 1.260344386100769, 1.5401318073272705, 1.6720627546310425, 2.336913585662842, 1.9787050485610962, 2.3948135375976562, 1.8047114610671997, 1.3032636642456055, 1.145747184753418, 1.6341732740402222, 2.1720876693725586, 1.868072509765625, 2.097315788269043, 1.8485099077224731, 2.4947328567504883, 1.478377342224121, 1.8285021781921387, 2.366436004638672, 2.040806770324707, 2.7071292400360107, 2.250366449356079, 2.1879894733428955, 2.237913131713867, 2.9724457263946533, 3.2604763507843018, 2.2528982162475586, 2.569121837615967, 2.1535303592681885, 1.4571374654769897, 2.68174147605896, 1.7503877878189087, 1.5114392042160034, 2.7664177417755127, 1.5382708311080933, 1.919486165046692, 1.6535367965698242, 1.9519282579421997, 1.3309621810913086, 2.261497974395752, 1.683048963546753, 2.4188714027404785, 1.996932029724121, 2.4787111282348633, 2.1418581008911133, 1.3697978258132935, 1.4716538190841675, 3.324786901473999, 1.6676130294799805, 3.3026702404022217, 1.7818126678466797, 2.8831377029418945, 2.9917328357696533, 2.2328250408172607, 1.3423376083374023, 2.382632255554199, 1.8568792343139648, 1.3383092880249023, 2.2862024307250977, 2.7748119831085205, 1.0406006574630737, 0.7815340757369995, 1.1905841827392578, 1.9859310388565063, 2.1047914028167725, 1.587483286857605, 1.9813145399093628, 2.0913238525390625, 1.7294645309448242, 2.256134510040283, 2.819580078125, 2.5808651447296143, 1.706097960472107, 1.5950231552124023, 1.538779377937317, 1.9336869716644287, 2.6547694206237793, 2.484665870666504, 2.2158734798431396, 2.42122483253479, 1.4701337814331055, 1.805769920349121, 2.074253559112549, 1.9861478805541992, 1.9460152387619019, 3.4329752922058105, 1.9267404079437256, 2.0903074741363525, 1.4257515668869019, 1.8527382612228394, 1.5840259790420532, 2.056389331817627, 2.4022035598754883, 1.3540438413619995, 1.7539403438568115, 2.6476335525512695, 2.3062617778778076, 1.8885908126831055, 2.914231538772583, 2.498830795288086, 1.523573875427246, 1.5230224132537842, 2.257845163345337, 1.2165946960449219, 2.3259658813476562, 2.7010509967803955, 1.4351814985275269, 1.3218488693237305, 2.343621253967285, 1.9324188232421875, 1.814570426940918, 2.3531150817871094, 1.7901611328125, 2.3522634506225586, 2.1361169815063477, 1.7326709032058716, 2.829352617263794, 1.5239477157592773, 2.22613263130188, 2.2438321113586426, 1.738558053970337, 0.9259567260742188, 3.2585113048553467, 1.65092933177948, 1.9655810594558716, 2.151900291442871, 1.9877086877822876, 1.6281081438064575, 1.635493278503418, 2.5811188220977783, 2.35697078704834, 2.7902438640594482, 2.7578954696655273, 1.717633605003357, 1.0208977460861206, 2.8036346435546875, 2.0978028774261475, 1.8741735219955444, 1.9069689512252808, 2.6806511878967285, 1.7357652187347412, 2.2764196395874023, 1.8900258541107178, 1.3033661842346191, 2.594860553741455, 1.9342153072357178, 1.5468146800994873, 2.3772706985473633, 2.0090343952178955, 2.1363158226013184, 2.499607801437378, 2.827983856201172, 2.8951351642608643, 2.8656556606292725, 2.453464984893799, 2.0053069591522217, 1.751545786857605, 1.000666856765747, 2.7535083293914795, 0.9667498469352722, 2.3064911365509033, 1.1371822357177734, 2.467698574066162, 2.2334799766540527, 1.8840818405151367, 1.2791088819503784, 2.096858024597168, 1.536596655845642, 1.5862600803375244, 1.8167771100997925, 1.5788679122924805, 3.8660051822662354, 1.8197487592697144, 2.9842381477355957, 1.5861862897872925, 2.252298593521118, 2.5622198581695557, 1.769683837890625, 2.251230001449585, 2.161137580871582, 2.138310432434082, 2.265730857849121, 2.8147125244140625, 2.036609172821045, 1.7759859561920166, 2.686816453933716, 2.631765127182007, 1.271594762802124, 2.22513747215271, 2.115978717803955, 1.9726940393447876, 1.8401060104370117, 1.7321362495422363, 2.205338478088379, 2.544976234436035, 1.7528910636901855, 1.4734183549880981, 1.4603933095932007, 1.89346444606781, 1.4992226362228394, 2.19509220123291, 2.3716516494750977, 1.3414121866226196, 2.602720260620117, 1.6235400438308716, 1.5270636081695557, 2.2633614540100098, 2.581662178039551, 2.0687856674194336, 2.3163325786590576, 1.0638024806976318, 2.483430862426758, 2.027777671813965, 1.6877754926681519, 1.7485512495040894, 1.0406484603881836, 1.461506962776184, 0.8426389694213867, 2.8473217487335205, 2.4830944538116455, 1.5565768480300903, 1.8479692935943604, 1.5360167026519775, 2.1066946983337402, 0.9444950819015503, 2.393285036087036, 2.475208044052124, 2.863865852355957, 2.4542770385742188, 2.7082414627075195, 2.4529542922973633, 2.23146915435791, 1.3277959823608398, 2.7310423851013184, 2.5411009788513184, 1.2782506942749023, 1.5677803754806519, 2.8971471786499023, 2.4919395446777344, 1.8266834020614624, 2.12235951423645, 1.2724822759628296, 1.57732093334198, 1.501524567604065, 1.9095486402511597, 3.0798888206481934, 2.5283758640289307, 1.7923437356948853, 2.613482713699341, 1.5217971801757812, 2.53971004486084, 2.927478075027466, 2.815401315689087, 2.027106285095215, 1.8792001008987427, 1.9081487655639648, 2.524369478225708, 1.4253873825073242, 1.8648287057876587, 1.9415487051010132, 1.6455886363983154, 2.606372117996216, 2.222966194152832, 1.4729479551315308, 1.5761996507644653, 2.75941801071167, 2.027660846710205, 2.882373809814453, 1.5721443891525269, 2.0655531883239746, 1.512876272201538, 2.5152547359466553, 1.7211097478866577, 1.6335210800170898, 1.2700481414794922, 2.0512921810150146, 2.2160537242889404, 1.7679604291915894, 0.0195537731051445, 0.021164696663618088, 0.13268493115901947, 0.02681864984333515, 0.12665021419525146, 0.14951689541339874, 0.021043209359049797, 0.019600093364715576, 0.04028056934475899, 0.13340497016906738, 0.04565102607011795, 0.04199402406811714, 0.00595868332311511, 0.06365934014320374, 0.1355220228433609, 0.024497568607330322, 0.10280518978834152, 0.06120222806930542, 0.13372713327407837, 0.017255844548344612, 0.05734992027282715, 0.08335676789283752, 0.06562650948762894, 0.060107287019491196, 0.07994072884321213, 0.0418490394949913, 0.09111474454402924, 0.06900933384895325, 0.07635726034641266, 0.12797172367572784, 0.057892583310604095, 0.02363092452287674, 0.07807949185371399, 0.03277233988046646, 0.07051347941160202, 0.05602818354964256, 0.05168135464191437, 0.15346582233905792, 0.06274166703224182, 0.09036412835121155, 0.027202563360333443, 0.04135442152619362, 0.07112640887498856, 0.05161714553833008, 0.04658610373735428, 0.09507006406784058, 0.10455905646085739, 0.18032805621623993, 0.1425156593322754, 0.050116974860429764, 0.12434881925582886, 0.05389221012592316, 0.09759066253900528, 0.08675616979598999, 0.06036477908492088, 0.10492273420095444, 0.08749385923147202, 0.08909111469984055, 0.07056055963039398, 0.019470512866973877, 0.09076422452926636, 0.03061574697494507, 0.06100223585963249, 0.027201073244214058, 0.049560725688934326, 0.12184131145477295, 0.0745965912938118, 0.12230502814054489, 0.061931051313877106, 0.0854005217552185, 0.0791134312748909, 0.12757249176502228, 0.03164832293987274, 0.047223929315805435, 0.052846964448690414, 0.03623254597187042, 0.10165385901927948, 0.07276491820812225, 0.08863013982772827, 0.10506515949964523, 0.11941181123256683, 0.09807233512401581, 0.012924307025969028, 0.13470883667469025, 0.03022838942706585, 0.06936666369438171, 0.07448840141296387, 0.06301945447921753, 0.04506219923496246, 0.11552474647760391, 0.08909029513597488, 0.07993748784065247, 0.08587712049484253, 0.09701446443796158, 0.022967100143432617, 0.10650326311588287, 0.05729200318455696, 0.02537391148507595, 0.011211504228413105, 0.08851619809865952, 0.09329129755496979, 0.0815664678812027, 0.14012816548347473, 0.1591343879699707, 0.052768245339393616, 0.08393782377243042, 0.0908399149775505, 0.09786774218082428, 0.08801063150167465, 0.12285789102315903, 0.03408723697066307, 0.03443654999136925, 0.10351567715406418, 0.09820237010717392, 0.0012349385069683194, 0.03363330289721489, 0.05983537435531616, 0.11652453243732452, 0.14408425986766815, 0.0312882736325264, 0.0788719654083252, 0.09140634536743164, 0.10416185110807419, 0.04777102544903755, 0.07754404842853546, 0.027996856719255447, 0.11236793547868729, 0.18923528492450714, 0.02387937530875206, 0.06258042901754379, 0.06257183849811554, 0.025984734296798706, 0.018729278817772865, 0.11330002546310425, 0.06640177965164185, 0.04339058697223663, 0.03552832826972008, 0.03243463486433029, 0.10387308150529861, 0.05969845503568649, 0.11446912586688995, 0.05801820755004883, 0.05011738836765289, 0.13136233389377594, 0.06746207922697067, 0.04704226553440094, 0.09643646329641342, 0.16622550785541534, 0.02890399843454361, 0.17218229174613953, 0.0020430278964340687, 0.08575475215911865, 0.12504853308200836, 0.05017288401722908, 0.024177083745598793, 0.11425900459289551, 0.02497285045683384, 0.16638299822807312, 0.06696207076311111, 0.05626709759235382, 0.08715671300888062, 0.0174562931060791, 0.04866291955113411, 0.06668579578399658, 0.044710833579301834, 0.10293769836425781, 0.056254275143146515, 0.12093538790941238, 0.0657040923833847, 0.11417937278747559, 0.08231382817029953, 0.12954194843769073, 0.05992913246154785, 0.13673396408557892, 0.09089929610490799, 0.09410911053419113, 0.06141257286071777, 0.03952610492706299, 0.05086316540837288, 0.07500213384628296, 0.06182875111699104, 0.1276348978281021, 0.05767238140106201, 0.07264671474695206, 0.06346864253282547, 0.048777107149362564, 0.06343661993741989, 0.014492477290332317, 0.05093113332986832, 0.10786233842372894, 0.0420578196644783, 0.05874035879969597, 0.0814557820558548, 0.10513448715209961, 0.07883777469396591, 0.022732466459274292, 0.07431197911500931, 0.07182786613702774, 0.14309188723564148, 0.08780592679977417, 0.05139429122209549, 0.08465705811977386, 0.07220955938100815, 0.05598646402359009, 0.06844836473464966, 0.21260949969291687, 0.05959778651595116, 0.12334653735160828, 0.12798936665058136, 0.07305387407541275, 0.13540877401828766, 0.08169852942228317, 0.1441013216972351, 0.13925433158874512, 0.05871674790978432, 0.0983889177441597, 0.08871406316757202, 0.13260449469089508, 0.0920116975903511, 0.09604937583208084, 0.10938222706317902, 0.09303342550992966, 0.12662242352962494, 0.1228213831782341, 0.11994004249572754, 0.037639960646629333, 0.11974503844976425, 0.1010124683380127, 0.12483108043670654, 0.07680079340934753, 0.04935700446367264, 0.07106264680624008, 0.10189133137464523, 0.07082803547382355, 0.09284466505050659, 0.06108136102557182, 0.07137864083051682, 0.07190753519535065, 0.050248581916093826, 0.015530109405517578, 0.09346050024032593, 0.10419213771820068, 0.07273329794406891, 0.08783691376447678, 0.06599064916372299, 0.0919836014509201, 0.09681423008441925, 0.03640657663345337, 0.009273089468479156, 0.08607392758131027, 0.05362064391374588, 0.07268548011779785, 0.1378222554922104, 0.1448020339012146, 0.10710912197828293, 0.11741077154874802, 0.06599825620651245, 0.04580189660191536, 0.1792374700307846, 0.0681101530790329, 0.0815843865275383, 0.1014719009399414, 0.04294729232788086, 0.04484844207763672, 0.053719814866781235, 0.15150271356105804, 0.09057102352380753, 0.06116343289613724, 0.11875157803297043, 0.14539660513401031, 0.12173175811767578, 0.07280346006155014, 0.1599111557006836, 0.09017419815063477, 0.10033950209617615, 0.07846373319625854, 0.02865087427198887, 0.07836033403873444, 0.04409288242459297, 0.02681986801326275, 0.06871172040700912, 0.05733419209718704, 0.051761507987976074, 0.07511501014232635, 0.08911914378404617, 0.1220020055770874, 0.07418403774499893, 0.1260041743516922, 0.11256235092878342, 0.05338530242443085, 0.10701626539230347, 0.08334822207689285, 0.019532376900315285, 0.06520262360572815, 0.0841754823923111, 0.10993246734142303, 0.10905753821134567, 0.12739503383636475, 0.10948246717453003, 0.10045675933361053, 0.20319464802742004, 0.7241454124450684, 0.596412718296051, 0.2714717388153076, 0.19944369792938232, 0.9839615225791931, 0.9133816957473755, 0.5986883640289307, 0.2978613078594208, 0.5255172848701477, 0.5954054594039917, 0.2593297064304352, 0.6816055178642273, 0.6716038584709167, 0.35644569993019104, 0.3932720720767975, 0.4282085597515106, 0.6206322312355042, 0.17267532646656036, 0.3246813118457794, 0.37346306443214417, 0.20817558467388153, 0.4112098217010498, 0.282577782869339, 0.35925012826919556, 0.3343343734741211, 0.2815607488155365, 0.6093510389328003, 0.4561348557472229, 0.44113194942474365, 0.496969074010849, 0.3175739347934723, 0.24616684019565582, 0.3641223907470703, 0.516594648361206, 0.7021059989929199, 0.3894713521003723, 0.3357048034667969, 0.25711771845817566, 0.47455763816833496, 0.4221912920475006, 0.6337293386459351, 0.7433302998542786, 0.3615606725215912, 0.3185407221317291, 0.6065343618392944, 0.720707356929779, 0.6664876937866211, 0.3098813593387604, 0.37008315324783325, 0.32262706756591797, 0.6778184175491333, 0.2926350235939026, 0.11311514675617218, 0.4146016836166382, 0.26343992352485657, 0.4011918604373932, 0.7931736707687378, 0.5481564998626709, 0.3082456886768341, 0.5134595632553101, 0.5664635300636292, 0.7625439167022705, 0.422229528427124, 0.9523095488548279, 0.25509023666381836, 0.777584969997406, 0.47886979579925537, 0.3503904938697815, 0.423628568649292, 0.43861865997314453, 0.2170620709657669, 0.89077228307724, 0.3602646589279175, 0.3314778804779053, 0.5357954502105713, 0.3896494209766388, 0.2714667022228241, 0.2943387031555176, 0.07811273634433746, 0.24149468541145325, 0.08178170025348663, 0.37103310227394104, 0.5757336616516113, 0.9349886178970337, 1.2150824069976807, 0.5469900369644165, 0.30434221029281616, 0.3234683871269226, 0.8213664293289185, 0.2562007009983063, 0.6712458729743958, 0.531292200088501, 0.37744107842445374, 0.5759920477867126, 0.17118938267230988, 0.36420756578445435, 0.5623398423194885, 0.12100128084421158, 0.9597184062004089, 0.47705426812171936, 0.6973757743835449, 0.24006156623363495, 0.4616917073726654, 0.37720203399658203, 0.7111456394195557, 0.42433348298072815, 0.46701765060424805, 0.9496280550956726, 0.5816828608512878, 0.347161203622818, 0.4851837158203125, 0.47400394082069397, 0.3993428349494934, 0.31915485858917236, 0.8046898245811462, 0.5591366291046143, 0.6531941294670105, 0.3188270330429077, 0.4023175835609436, 0.4022141993045807, 0.40164047479629517, 0.3814823031425476, 0.5293402671813965, 0.3016703426837921, 0.6653742790222168, 0.4199622571468353, 0.5082508325576782, 0.6391404867172241, 0.1542603224515915, 0.20047466456890106, 0.49530741572380066, 0.8766600489616394, 0.5595016479492188, 0.38670217990875244, 0.5519919991493225, 0.4276592433452606, 0.83257657289505, 0.7840920686721802, 0.5333924889564514, 0.43656501173973083, 0.4239937365055084, 0.7821251749992371, 0.2966294288635254, 0.5126809477806091, 0.4256417751312256, 0.4293042719364166, 1.1331630945205688, 0.5198972225189209, 0.6502960920333862, 0.4080756902694702, 0.7046514749526978, 0.3628349304199219, 0.8095481395721436, 0.26654738187789917, 0.41069307923316956, 0.36854633688926697, 0.30469346046447754, 0.48686304688453674, 0.5918896794319153, 0.4124796986579895, 0.3662385046482086, 0.6907891631126404, 0.4224835932254791, 0.5901744961738586, 0.2990650236606598, 0.6637086272239685, 0.5586204528808594, 0.5801559090614319, 0.37702807784080505, 0.5203226208686829, 0.3882843554019928, 0.5250762104988098, 0.7518009543418884, 0.33492323756217957, 0.37510770559310913, 0.5824424028396606, 0.4682837128639221, 0.7483121156692505, 0.4337967336177826, 0.11654622852802277, 0.2818450629711151, 0.34158778190612793, 0.409667432308197, 0.7776579856872559, 0.4533300995826721, 0.712573766708374, 0.10605663061141968, 0.448403924703598, 0.40912261605262756, 0.8855618238449097, 0.6290990114212036, 0.29283320903778076, 0.2657950222492218, 0.6732510328292847, 0.4195132255554199, 0.22716231644153595, 0.8296200633049011, 0.3829461634159088, 0.27106884121894836, 0.8459653854370117, 0.5080248117446899, 0.23142264783382416, 0.5859240889549255, 0.47712913155555725, 0.26930639147758484, 0.7850980758666992, 0.6372480392456055, 0.4042280614376068, 0.6032763719558716, 0.5519981384277344, 0.62492835521698, 0.5044432878494263, 0.257021427154541, 0.6172840595245361, 0.3093358278274536, 0.4269012212753296, 0.6159133911132812, 0.11089476943016052, 0.555506706237793, 0.44225573539733887, 0.7017185688018799, 0.5797215700149536, 0.33365538716316223, 0.6139711737632751, 0.675944983959198, 0.11349523067474365, 0.5554309487342834, 0.3464471399784088, 0.3775772154331207, 0.5126065611839294, 0.27705302834510803, 0.5973788499832153, 0.22229230403900146, 0.7708871364593506, 0.7066075205802917, 0.33578720688819885, 0.2432623952627182, 0.48559504747390747, 1.1209869384765625, 0.26500263810157776, 0.5087435245513916, 0.18913912773132324, 0.607370913028717, 0.6675623059272766, 0.7442947030067444, 0.2527775466442108, 0.4120989441871643, 0.2732676565647125, 0.3019045293331146, 0.18914644420146942, 0.48198413848876953, 0.5802901387214661, 0.583457887172699, 0.3499579429626465, 0.15672121942043304, 0.5537704229354858, 0.6550621390342712, 0.6247619986534119, 0.41227057576179504, 0.42046722769737244, 0.19954554736614227, 0.6529231071472168, 0.5287713408470154, 0.626398503780365, 0.3242642283439636, 0.5220203995704651, 0.7661712765693665, 0.500820517539978, 0.3579973578453064, 0.589702844619751, 0.48410338163375854, 0.47324338555336, 0.7043388485908508, 0.3816775381565094, 0.6654801964759827, 0.28698045015335083, 0.44707489013671875, 0.5005118250846863, 0.524817943572998, 0.5694351196289062, 0.685746967792511, 0.233216792345047, 0.21547812223434448, 0.43779289722442627, 0.5194752216339111, 0.44975337386131287, 0.5635698437690735, 0.7539858818054199, 0.6831898093223572, 0.5474647283554077, 0.285812109708786, 0.7447106242179871, 0.41136470437049866, 0.21593046188354492, 0.4577058255672455, 0.7135230898857117, 0.4762730300426483, 0.6534982323646545, 0.5465042591094971, 16.336761474609375, 94.3121109008789, 44.3590087890625, 20.26972770690918, 41.59577941894531, 41.09565734863281, 42.28120040893555, 14.016204833984375, 14.572908401489258, 41.8364143371582, 37.41612243652344, 19.817529678344727, 13.658447265625, 91.0107421875, 56.8404541015625, 89.0412368774414, 13.967138290405273, 12.82436752319336, 11.937165260314941, 27.569091796875, 30.995670318603516, 35.27262878417969, 46.19350051879883, 19.88606071472168, 28.647117614746094, 16.105915069580078, 41.13654327392578, 12.289276123046875, 19.7242431640625, 35.657005310058594, 32.93353271484375, 75.9642333984375, 18.38897705078125, 60.791072845458984, 25.743871688842773, 82.161376953125, 63.47956848144531, 17.11494255065918, 14.318696022033691, 39.39874267578125, 11.37103271484375, 49.77191925048828, 43.3131103515625, 31.69097900390625, 64.18353271484375, 20.470687866210938, 67.01625061035156, 78.70696258544922, 19.23728370666504, 76.67874145507812, 26.542104721069336, 11.261871337890625, 39.69803237915039, 28.239715576171875, 71.02694702148438, 66.57389831542969, 45.4085693359375, 37.05674743652344, 14.666152000427246, 10.031420707702637, 29.445341110229492, 21.800443649291992, 54.15911865234375, 48.585472106933594, 69.23283386230469, 25.773849487304688, 39.24289321899414, 50.0858154296875, 50.54829025268555, 29.197362899780273, 13.747909545898438, 16.68751335144043, 22.697677612304688, 18.45843505859375, 10.127711296081543, 20.29816436767578, 32.02215576171875, 46.4537353515625, 22.866806030273438, 11.3665771484375, 14.195108413696289, 17.370363235473633, 9.30476188659668, 46.846736907958984, 13.070378303527832, 24.999679565429688, 62.76727294921875, 17.23748779296875, 41.97340774536133, 65.97335052490234, 15.851698875427246, 13.41817855834961, 24.0814208984375, 39.45290756225586, 16.687591552734375, 18.377426147460938, 36.45205307006836, 75.67237091064453, 59.01582717895508, 56.350364685058594, 15.924199104309082, 51.35948181152344, 23.41064453125, 38.61215591430664, 15.229291915893555, 13.222975730895996, 72.90544128417969, 29.312469482421875, 24.791351318359375, 40.908138275146484, 16.535812377929688, 41.166072845458984, 25.679046630859375, 12.51531982421875, 22.569915771484375, 69.42477416992188, 67.3155517578125, 93.59158325195312, 45.15748977661133, 61.16483688354492, 12.258346557617188, 73.64683532714844, 17.87548828125, 95.16677856445312, 8.105141639709473, 53.8067626953125, 46.61009216308594, 94.0873794555664, 28.778226852416992, 14.18939208984375, 83.5727310180664, 17.431671142578125, 17.214111328125, 17.73175048828125, 20.39674186706543, 12.374098777770996, 16.24334716796875, 15.651290893554688, 28.311203002929688, 20.671798706054688, 12.690765380859375, 99.01554107666016, 62.45341110229492, 33.67262268066406, 122.04898071289062, 15.20445728302002, 25.710233688354492, 10.789307594299316, 76.469482421875, 46.58205032348633, 29.384979248046875, 66.94108581542969, 20.178680419921875, 81.41612243652344, 75.3970947265625, 14.457587242126465, 33.69044494628906, 14.79684066772461, 61.125526428222656, 19.013208389282227, 22.618255615234375, 31.384061813354492, 13.741825103759766, 36.7353515625, 33.3569221496582, 13.981002807617188, 23.500732421875, 21.9796142578125, 37.627197265625, 77.9273681640625, 45.75714874267578, 12.7767333984375, 23.078372955322266, 82.47408294677734, 12.10009765625, 21.103805541992188, 16.28643798828125, 17.88013458251953, 43.87732696533203, 77.7852783203125, 22.497953414916992, 58.504486083984375, 30.863842010498047, 17.3179988861084, 23.333297729492188, 31.459030151367188, 52.15346908569336, 39.428855895996094, 17.668563842773438, 10.044923782348633, 17.51841926574707, 37.17801284790039, 12.996212005615234, 33.33413314819336, 25.27443504333496, 35.13103103637695, 58.18080520629883, 19.803955078125, 48.28152084350586, 60.14768600463867, 16.034523010253906, 24.979022979736328, 60.45263671875, 93.2596435546875, 12.869508743286133, 28.4859619140625, 51.057586669921875, 22.43951416015625, 23.54400634765625, 31.559818267822266, 51.90000534057617, 22.072694778442383, 21.878662109375, 7.022974491119385, 24.01521873474121, 20.776540756225586, 33.310150146484375, 121.26939392089844, 52.866756439208984, 17.411222457885742, 13.4095458984375, 9.55682373046875, 27.05202865600586, 93.70792388916016, 77.86029052734375, 55.407772064208984, 111.189208984375, 13.49810791015625, 17.361785888671875, 30.308944702148438, 44.67987060546875, 24.28790283203125, 11.380069732666016, 9.037261962890625, 48.278411865234375, 31.541776657104492, 28.691312789916992, 70.40480041503906, 30.389554977416992, 13.128204345703125, 24.634262084960938, 111.88796997070312, 92.55889129638672, 49.71742248535156, 33.09242630004883, 17.384119033813477, 11.921645164489746, 16.873077392578125, 92.92255401611328, 43.531829833984375, 34.07930374145508, 8.073806762695312, 26.342254638671875, 17.731475830078125, 53.457122802734375, 68.64334106445312, 21.193056106567383, 10.28509521484375, 60.44785690307617, 47.919315338134766, 40.65542221069336, 15.785614013671875, 22.31926918029785, 12.571521759033203, 22.91400146484375, 39.2886848449707, 44.84384536743164, 22.053190231323242, 9.898483276367188, 13.574066162109375, 61.698387145996094, 11.633056640625, 25.912071228027344, 71.11225128173828, 144.0865020751953, 10.245196342468262, 103.66773223876953, 89.849853515625, 19.31764030456543, 70.68052673339844, 28.502187728881836, 53.68701934814453, 65.67919921875, 8.341729164123535, 38.94938278198242, 44.83562088012695, 72.7364501953125, 48.86799621582031, 15.4664306640625, 13.589244842529297, 40.646141052246094, 41.274749755859375, 64.0438232421875, 15.60223388671875, 11.897625923156738, 30.4169921875, 117.5940170288086, 9.535293579101562, 73.28567504882812, 30.9158935546875, 1.905959129333496, 2.5097286701202393, 1.857235074043274, 1.008745551109314, 2.2393202781677246, 2.289548397064209, 1.5476311445236206, 1.5294082164764404, 1.2606018781661987, 2.277851104736328, 2.166090965270996, 2.6734983921051025, 3.21928334236145, 1.7916860580444336, 1.3785218000411987, 1.9080079793930054, 1.8066664934158325, 1.5468800067901611, 1.449921727180481, 2.621210813522339, 1.6156606674194336, 2.1134557723999023, 1.7545340061187744, 1.8036164045333862, 1.6682344675064087, 2.4078078269958496, 1.885451316833496, 2.1969807147979736, 2.6423070430755615, 1.8324326276779175, 1.275233268737793, 1.5359433889389038, 3.8859570026397705, 3.087298631668091, 2.7201449871063232, 1.18101966381073, 1.6756939888000488, 1.1032323837280273, 1.512715220451355, 1.7910014390945435, 2.1145105361938477, 1.5183457136154175, 1.3960790634155273, 1.681996464729309, 2.142901659011841, 1.8019132614135742, 2.9164745807647705, 2.4957456588745117, 2.7260632514953613, 1.4827370643615723, 1.492897868156433, 2.423980712890625, 1.7095882892608643, 2.0382978916168213, 2.049563407897949, 2.6493444442749023, 2.2517635822296143, 2.171149253845215, 2.843395948410034, 1.6634554862976074, 2.7075157165527344, 1.7878446578979492, 1.6636686325073242, 2.720499277114868, 1.2975744009017944, 1.6953108310699463, 1.414544939994812, 2.4361014366149902, 2.2768595218658447, 1.8560574054718018, 2.8808910846710205, 1.525909185409546, 1.803436279296875, 1.5682495832443237, 2.502009391784668, 1.52214515209198, 3.312373161315918, 1.448081612586975, 2.397883892059326, 3.236877918243408, 1.9474416971206665, 2.6910195350646973, 1.9816617965698242, 1.3700112104415894, 1.5418670177459717, 2.244751214981079, 1.2571525573730469, 2.606278657913208, 1.6883623600006104, 3.506016731262207, 1.928385615348816, 1.9611300230026245, 1.4099125862121582, 2.065545082092285, 1.940704584121704, 1.9218114614486694, 2.0897905826568604, 2.1597812175750732, 2.3938186168670654, 3.201674699783325, 2.276127815246582, 2.748291492462158, 1.8131513595581055, 1.761014461517334, 2.4279165267944336, 1.2227363586425781, 2.464104652404785, 1.9794340133666992, 2.176133871078491, 1.273579478263855, 1.2105110883712769, 0.5285038352012634, 2.0083208084106445, 1.7298965454101562, 1.803339958190918, 1.4052058458328247, 1.6900858879089355, 2.0645015239715576, 1.821816325187683, 1.6280622482299805, 2.471605062484741, 1.626692771911621, 2.2153759002685547, 1.906022310256958, 2.1163809299468994, 1.6757726669311523, 2.610377073287964, 1.9534964561462402, 2.804157257080078, 1.164284586906433, 2.1502809524536133, 2.846707582473755, 2.0612270832061768, 1.4990395307540894, 1.9886083602905273, 2.0082132816314697, 1.9429775476455688, 2.284482479095459, 2.921360969543457, 2.1331777572631836, 1.570241093635559, 1.81639564037323, 2.9673984050750732, 2.004045248031616, 1.673880934715271, 2.5737717151641846, 2.739797353744507, 2.477238655090332, 1.6789599657058716, 1.2154968976974487, 1.5237579345703125, 2.094414234161377, 1.6134214401245117, 1.7845231294631958, 1.5085402727127075, 1.5598211288452148, 2.782414436340332, 2.360970973968506, 1.2876349687576294, 1.408797264099121, 1.3930596113204956, 1.3394742012023926, 2.5644099712371826, 2.7340004444122314, 1.7547566890716553, 2.0021681785583496, 2.53250789642334, 1.8810560703277588, 2.0962369441986084, 1.609780192375183, 2.3117616176605225, 1.451810598373413, 1.5240205526351929, 1.621638298034668, 3.512782096862793, 1.2196569442749023, 2.00974178314209, 2.3940584659576416, 1.6251401901245117, 2.8318278789520264, 2.7924578189849854, 1.5072078704833984, 2.3139724731445312, 2.7678489685058594, 1.2083284854888916, 1.9751633405685425, 2.5277774333953857, 2.0652647018432617, 1.510584831237793, 2.5013437271118164, 2.0468666553497314, 2.6021578311920166, 1.2011536359786987, 2.3372268676757812, 1.4060635566711426, 2.6164464950561523, 1.335550308227539, 2.2366976737976074, 1.1116079092025757, 1.6875905990600586, 1.2212096452713013, 1.9628896713256836, 2.706697940826416, 1.901383876800537, 1.684064269065857, 1.2987256050109863, 3.171281099319458, 1.587458610534668, 2.2203874588012695, 2.0668725967407227, 1.110182762145996, 1.9901076555252075, 1.8545937538146973, 1.9026122093200684, 2.1955788135528564, 2.0913636684417725, 3.1570329666137695, 2.564893960952759, 2.5728654861450195, 1.398232340812683, 3.4061241149902344, 1.7467316389083862, 2.109618902206421, 2.773747444152832, 2.617856979370117, 1.7043187618255615, 1.3006829023361206, 2.89089298248291, 1.550209879875183, 2.4267969131469727, 2.4020352363586426, 2.3510048389434814, 2.363335609436035, 2.5132904052734375, 2.2092392444610596, 2.071247100830078, 2.0982961654663086, 0.9025769829750061, 1.799769401550293, 2.446133613586426, 2.353760242462158, 1.6008423566818237, 1.9715099334716797, 1.6558468341827393, 1.3085994720458984, 1.9441779851913452, 1.7517975568771362, 2.5368547439575195, 2.548750638961792, 1.946105718612671, 1.6599382162094116, 1.7924456596374512, 1.3906351327896118, 2.2005205154418945, 0.7114324569702148, 1.879391074180603, 1.8776885271072388, 1.684243083000183, 2.6608855724334717, 2.586909055709839, 2.639422655105591, 2.2387518882751465, 2.3993422985076904, 1.9852303266525269, 1.491657018661499, 1.9671295881271362, 1.2037690877914429, 1.7116974592208862, 1.6429767608642578, 2.246434211730957, 2.149264097213745, 1.8811089992523193, 2.36026930809021, 1.4941364526748657, 3.327336311340332, 1.8940621614456177, 2.039919853210449, 1.8531619310379028, 2.330803871154785, 1.8966721296310425, 1.6042650938034058, 2.28572416305542, 2.0573158264160156, 2.303292989730835, 1.4885224103927612, 2.8615660667419434, 1.8909233808517456, 2.0321383476257324, 2.815277576446533, 2.01240873336792, 1.4503639936447144, 1.742065191268921, 1.429848313331604, 2.0343828201293945, 1.9981212615966797, 2.7145302295684814, 1.542948842048645, 1.4713897705078125, 1.0348862409591675, 2.7458338737487793, 0.08028491586446762, 0.01713467575609684, 0.027786076068878174, 0.0861290693283081, 0.0, 0.052471693605184555, 0.16810479760169983, 0.02373141050338745, 0.0589735321700573, 0.10970786958932877, 0.09511939436197281, 0.03189357742667198, 0.07767385244369507, 0.06933140009641647, 0.04614076390862465, 0.06616578996181488, 0.018024992197752, 0.07056566327810287, 0.047703053802251816, 0.15727120637893677, 0.10097092390060425, 0.024300098419189453, 0.05508030951023102, 0.14053845405578613, 0.11533942818641663, 0.11094237118959427, 0.07941997051239014, 0.10193648189306259, 0.12598074972629547, 0.049836840480566025, 0.09903866797685623, 0.0806494951248169, 0.08810630440711975, 0.11726593971252441, 0.07482486218214035, 0.04321868345141411, 0.017174148932099342, 0.07483787089586258, 0.11310010403394699, 0.10285245627164841, 0.10098251700401306, 0.04953094199299812, 0.031417541205883026, 0.09486135095357895, 0.03382551670074463, 0.09394445270299911, 0.06537765264511108, 0.050396084785461426, 0.17135772109031677, 0.023051032796502113, 0.08062778413295746, 0.12884150445461273, 0.1745542287826538, 0.07105902582406998, 0.06399112194776535, 0.03533785417675972, 0.03139662742614746, 0.0226060152053833, 0.0356568768620491, 0.05269992724061012, 0.05985143035650253, 0.06520562618970871, 0.02121640555560589, 0.05038364231586456, 0.09942267090082169, 0.17585213482379913, 0.051730334758758545, 0.04381180554628372, 0.14594444632530212, 0.07659056037664413, 0.06550854444503784, 0.045263901352882385, 0.1409313827753067, 0.02259439416229725, 0.07800358533859253, 0.056359175592660904, 0.03221053630113602, 0.066432423889637, 0.0873635858297348, 0.0927804708480835, 0.06403689831495285, 0.03659530729055405, 0.030096134170889854, 0.09329207986593246, 0.10800594091415405, 0.039903223514556885, 0.052141427993774414, 0.04174761101603508, 0.0350838378071785, 0.14643587172031403, 0.10730854421854019, 0.08381211757659912, 0.07260316610336304, 0.12771105766296387, 0.12977829575538635, 0.14111799001693726, 0.06791386008262634, 0.05540693551301956, 0.14694969356060028, 0.05924034118652344, 0.0970044657588005, 0.07227745652198792, 0.10058507323265076, 0.0619211420416832, 0.07605087757110596, 0.041962869465351105, 0.0753282755613327, 0.10095464438199997, 0.035108573734760284, 0.10227098315954208, 0.11271902173757553, 0.04208683967590332, 0.07895886898040771, 0.07897378504276276, 0.10366165637969971, 0.1366804987192154, 0.08301885426044464, 0.09471122175455093, 0.08253592252731323, 0.06476026773452759, 0.09156037867069244, 0.05863044783473015, 0.09737682342529297, 0.045886535197496414, 0.12798914313316345, 0.07282402366399765, 0.14479190111160278, 0.10144516825675964, 0.03668179735541344, 0.08997546881437302, 0.0710822269320488, 0.06763095408678055, 0.07157707214355469, 0.1015363484621048, 0.06280677765607834, 0.1000368595123291, 0.13958393037319183, 0.02605605497956276, 0.07572710514068604, 0.06133398413658142, 0.14121773838996887, 0.10575977712869644, 0.06957411766052246, 0.06762229651212692, 0.06785717606544495, 0.058576714247465134, 0.027432560920715332, 0.12880955636501312, 0.06222603842616081, 0.07452516257762909, 0.08495340496301651, 0.09374115616083145, 0.08448868244886398, 0.06951582431793213, 0.07119095325469971, 0.03725207597017288, 0.026286840438842773, 0.0399000383913517, 0.0516972541809082, 0.06471844762563705, 0.06630581617355347, 0.0661894679069519, 0.09616345912218094, 0.029750289395451546, 0.08233960717916489, 0.03127743676304817, 0.038476087152957916, 0.10701245069503784, 0.08689241856336594, 0.1215135008096695, 0.07621831446886063, 0.07544852048158646, 0.03446751832962036, 0.1341661661863327, 0.12651056051254272, 0.02333906665444374, 0.08696826547384262, 0.16263702511787415, 0.11292213201522827, 0.10929948836565018, 0.09108561277389526, 0.13249360024929047, 0.0777842327952385, 0.06996499747037888, 0.06584642082452774, 0.035818975418806076, 0.0665365606546402, 0.07750340551137924, 0.13148938119411469, 0.10675114393234253, 0.08506305515766144, 0.09748058021068573, 0.07064346969127655, 0.0998227670788765, 0.08338049054145813, 0.11945183575153351, 0.06478536128997803, 0.0731067955493927, 0.05879086256027222, 0.026764607056975365, 0.10284935683012009, 0.10611508041620255, 0.11484897136688232, 0.11021434515714645, 0.12409024685621262, 0.12764640152454376, 0.06780394911766052, 0.07918509840965271, 0.06281157582998276, 0.08015327900648117, 0.051473140716552734, 0.027849487960338593, 0.09503015130758286, 0.1598728746175766, 0.09601440280675888, 0.08056477457284927, 0.05758941173553467, 0.09066315740346909, 0.06339718401432037, 0.08779396861791611, 0.08158353716135025, 0.0661623477935791, 0.03368660435080528, 0.05853214114904404, 0.11557281017303467, 0.04417942091822624, 0.040437765419483185, 0.11155896633863449, 0.14520956575870514, 0.06324099749326706, 0.07644660025835037, 0.04106642305850983, 0.06239922717213631, 0.1035301685333252, 0.049547307193279266, 0.05041313171386719, 0.1641351878643036, 0.09542834758758545, 0.07812009751796722, 0.09955400228500366, 0.07591038197278976, 0.0316820964217186, 0.13862687349319458, 0.13562893867492676, 0.09494023770093918, 0.09187865257263184, 0.05862431228160858, 0.08843129873275757, 0.07208660244941711, 0.03519999608397484, 0.15327197313308716, 0.10652884840965271, 0.13064152002334595, 0.09493625164031982, 0.07410933077335358, 0.053896255791187286, 0.1330396831035614, 0.046276796609163284, 0.10557237267494202, 0.10343382507562637, 0.0783013105392456, 0.09328550100326538, 0.02790379524230957, 0.10199608653783798, 0.07810240983963013, 0.0354420505464077, 0.09546525776386261, 0.04110610485076904, 0.13177341222763062, 0.06352068483829498, 0.03605940192937851, 0.18356448411941528, 0.07514781504869461, 0.07104449719190598, 0.09191542118787766, 0.10531719028949738, 0.06377620249986649, 0.07674358785152435, 0.042279720306396484, 0.11836179345846176, 0.078483946621418, 0.109748475253582, 0.08562401682138443, 0.03609854727983475, 0.08132040500640869, 0.06184924393892288, 0.08401262015104294, 0.08130431175231934, 0.12053445726633072, 0.11236739158630371, 0.16135306656360626, 0.06688561290502548, 0.04112976789474487, 0.03924748674035072, 0.10291093587875366, 0.03567332401871681, 0.043001770973205566, 0.09665550291538239, 0.09923097491264343, 0.05451416224241257, 0.41491127014160156, 0.38803550601005554, 0.2625540494918823, 0.6718924641609192, 0.6378154754638672, 0.7534180879592896, 0.576687216758728, 0.52597576379776, 0.4121924042701721, 0.347684383392334, 0.37051719427108765, 0.39498573541641235, 0.47654104232788086, 0.6855503916740417, 0.7737157940864563, 0.6683034896850586, 0.559580385684967, 0.7032544016838074, 0.6446471810340881, 0.014328226447105408, 0.7100022435188293, 0.16885513067245483, 0.5312535166740417, 0.43063512444496155, 0.624839186668396, 0.24899666011333466, 0.40657350420951843, 0.4318039119243622, 0.7110598683357239, 0.7566567659378052, 0.5507352352142334, 0.3460400700569153, 0.7960041165351868, 0.27957531809806824, 0.6670341491699219, 0.5397526025772095, 0.48777857422828674, 0.6087411642074585, 0.6931875348091125, 0.4567963182926178, 0.4648761749267578, 0.5302067995071411, 0.707902193069458, 0.3515368103981018, 0.30820977687835693, 0.5205716490745544, 0.3496555984020233, 0.29610198736190796, 0.30779868364334106, 0.3283374309539795, 0.19199931621551514, 0.8501675724983215, 0.5178663730621338, 0.6710224151611328, 0.3288848102092743, 0.7177724838256836, 0.5482335686683655, 0.6271147727966309, 0.4207857549190521, 0.39816442131996155, 0.856078028678894, 0.415741503238678, 0.810326337814331, 0.5658038854598999, 0.46440330147743225, 0.45402684807777405, 0.4248689115047455, 0.7730687260627747, 0.6691290140151978, 0.3951427638530731, 0.5017167329788208, 0.2522995173931122, 0.820941150188446, 0.5558326840400696, 0.34855055809020996, 0.2526598870754242, 0.5807023644447327, 0.5222957730293274, 0.462158739566803, 0.44939711689949036, 0.7541139721870422, 0.6946267485618591, 0.27561989426612854, 0.5498652458190918, 0.3308733403682709, 0.6534492373466492, 0.3884657919406891, 0.6940687298774719, 0.4146115779876709, 0.3076184093952179, 0.6464782357215881, 0.6560302376747131, 0.8430092930793762, 0.1918860524892807, 0.41312557458877563, 0.6861382722854614, 0.7476609349250793, 0.5673115253448486, 0.16098468005657196, 0.5612090826034546, 0.7046278119087219, 0.6604143381118774, 0.45037952065467834, 0.8355693817138672, 0.8565406799316406, 0.814947247505188, 0.6771178245544434, 0.36372095346450806, 1.0014170408248901, 0.4790242612361908, 0.4703550338745117, 0.812275230884552, 0.6845346093177795, 0.1895802766084671, 0.160472109913826, 0.33925315737724304, 0.49363523721694946, 0.5341243743896484, 0.20470504462718964, 0.24419978260993958, 0.4885208308696747, 0.44070807099342346, 0.5089021325111389, 0.3653586506843567, 1.0886273384094238, 0.49027949571609497, 1.1782069206237793, 0.1494475156068802, 0.5690807700157166, 0.4322591722011566, 0.5596031546592712, 0.6637513041496277, 0.3716283440589905, 0.4037344753742218, 0.5034869313240051, 0.2138284295797348, 0.2977328896522522, 0.7537826895713806, 0.3455674648284912, 0.5026884078979492, 0.5313756465911865, 0.3759079575538635, 0.6086084842681885, 0.3751128315925598, 0.2830539345741272, 0.3271718919277191, 0.5336735248565674, 0.742753803730011, 0.8624531626701355, 0.1815243512392044, 0.3300949037075043, 0.31209713220596313, 0.4812088906764984, 0.5798484086990356, 0.3331461250782013, 0.4907751679420471, 0.2479865550994873, 0.30156224966049194, 0.6194047927856445, 0.4905153512954712, 0.5243934988975525, 0.4814329743385315, 0.35042548179626465, 0.42656397819519043, 0.7100857496261597, 0.7372224926948547, 0.44113340973854065, 0.7859284281730652, 0.617699384689331, 0.4571058452129364, 0.2786716818809509, 0.7714360356330872, 0.6587049961090088, 1.0377291440963745, 0.4143749177455902, 0.3330062925815582, 0.456531822681427, 0.20469866693019867, 0.8158261179924011, 0.30051201581954956, 0.3223935663700104, 0.4213503301143646, 0.4419007897377014, 0.4423995912075043, 0.6360875368118286, 0.6974145174026489, 0.6700125932693481, 0.5329083800315857, 0.6443934440612793, 0.3982340395450592, 0.567520797252655, 0.571002721786499, 0.3994714319705963, 0.2204112559556961, 0.5523077249526978, 0.47645822167396545, 0.5391185879707336, 0.8277490139007568, 0.3446106016635895, 0.4638952612876892, 0.936882734298706, 0.710555374622345, 0.640082061290741, 0.9351269602775574, 0.29881930351257324, 0.3730327785015106, 0.7009074091911316, 0.18941569328308105, 0.37431150674819946, 0.7372296452522278, 0.9052746891975403, 0.46145591139793396, 0.4746520519256592, 0.3511025011539459, 0.6021206378936768, 0.6399156451225281, 0.553096354007721, 0.806423008441925, 0.7580615282058716, 0.6820549368858337, 0.9108845591545105, 0.4518457353115082, 0.516716718673706, 0.187405064702034, 0.8942678570747375, 0.8123695850372314, 0.6235603094100952, 0.5057459473609924, 0.3736666142940521, 0.5123395323753357, 0.584460973739624, 0.5399829149246216, 0.4881730079650879, 0.2052120417356491, 0.5148605108261108, 0.43493789434432983, 0.5433631539344788, 0.7265406847000122, 0.8261149525642395, 0.687292754650116, 0.8825052380561829, 0.5489696860313416, 0.4024336040019989, 0.44296973943710327, 0.5711989402770996, 0.3823803961277008, 0.4141370356082916, 0.5398594737052917, 0.3328894078731537, 0.4103584587574005, 0.42973029613494873, 0.5535889267921448, 0.3322701156139374, 0.581052839756012, 0.43583524227142334, 0.464215487241745, 0.5638169050216675, 0.7801582217216492, 0.8138901591300964, 0.5738429427146912, 0.801236093044281, 0.7091816663742065, 0.48654210567474365, 0.5830997228622437, 0.4412994980812073, 0.621476411819458, 0.2944031059741974, 0.7469009757041931, 0.18490727245807648, 0.6084813475608826, 0.25669437646865845, 0.4496125280857086, 0.47805777192115784, 0.4778502583503723, 0.5043036937713623, 0.6575475931167603, 0.2703282833099365, 0.5194599032402039, 0.3392503261566162, 0.35272541642189026, 0.5369266867637634, 0.6548078656196594, 0.46738725900650024, 0.781053364276886, 0.21551528573036194, 0.5011677145957947, 0.9480422139167786, 0.5297591090202332, 0.5737337470054626, 0.576231837272644, 0.47539424896240234, 0.4243943691253662, 0.5886949896812439, 0.4706435203552246, 0.5986336469650269, 0.7778410911560059, 0.6459094285964966, 0.4717384874820709, 0.5878868103027344, 0.974183201789856, 36.63648986816406, 80.42758178710938, 14.953309059143066, 58.30740737915039, 28.895477294921875, 39.59600830078125, 36.00386047363281, 73.58452606201172, 29.462717056274414, 75.71673583984375, 49.0242919921875, 46.687744140625, 27.98914909362793, 35.65272521972656, 31.19911003112793, 48.8533935546875, 53.2824592590332, 35.03078842163086, 32.35444641113281, 10.254931449890137, 64.48480224609375, 26.545555114746094, 29.996723175048828, 14.663735389709473, 86.55827331542969, 6.252288818359375, 31.58272933959961, 37.180145263671875, 26.540863037109375, 60.77793884277344, 17.794708251953125, 34.13970947265625, 29.102617263793945, 17.680633544921875, 34.53266143798828, 20.397308349609375, 119.6961669921875, 22.10711669921875, 11.01812744140625, 40.15359115600586, 17.40113639831543, 72.91986846923828, 29.598134994506836, 31.103055953979492, 19.17042350769043, 18.444549560546875, 52.694637298583984, 20.2303524017334, 28.47760009765625, 87.7850570678711, 16.05836296081543, 84.68695068359375, 40.95016098022461, 42.68410873413086, 18.681442260742188, 87.91962432861328, 30.963424682617188, 33.6370735168457, 47.19590759277344, 34.43690490722656, 15.516826629638672, 13.98011589050293, 18.74609375, 18.70464515686035, 32.29701232910156, 47.29378890991211, 129.2431640625, 46.6234130859375, 33.37540054321289, 36.71502685546875, 84.27264404296875, 23.102890014648438, 54.21601486206055, 48.38276290893555, 14.815443992614746, 20.417890548706055, 51.14384841918945, 52.35621643066406, 15.96795654296875, 91.95437622070312, 29.3682861328125, 17.58479118347168, 66.53475952148438, 57.353275299072266, 44.25117111206055, 102.16139221191406, 56.95947265625, 69.75869750976562, 17.957904815673828, 43.91123962402344, 65.162353515625, 14.15008544921875, 16.376144409179688, 89.676025390625, 38.04029083251953, 35.78862380981445, 24.30169677734375, 66.75350189208984, 16.997055053710938, 70.705322265625, 44.531063079833984, 54.87428665161133, 32.08242416381836, 43.10447311401367, 29.762357711791992, 32.7670783996582, 79.95257568359375, 59.10329055786133, 13.136260986328125, 24.19459342956543, 87.14604949951172, 66.216796875, 39.462860107421875, 40.95737838745117, 27.711332321166992, 48.05647277832031, 30.545501708984375, 11.009466171264648, 13.9847412109375, 80.779296875, 80.59883880615234, 44.49192428588867, 35.350616455078125, 20.39422607421875, 65.69613647460938, 27.318973541259766, 22.175048828125, 17.09199333190918, 11.58856201171875, 9.028159141540527, 43.7984619140625, 11.611647605895996, 38.04343795776367, 11.995217323303223, 16.49932861328125, 10.660858154296875, 16.58038330078125, 44.09765625, 39.47210693359375, 10.018875122070312, 56.872215270996094, 66.5084228515625, 67.36821746826172, 13.821441650390625, 68.92916870117188, 39.18422317504883, 60.7116584777832, 17.14251708984375, 40.37270736694336, 41.66910934448242, 42.58542251586914, 40.77446746826172, 18.425521850585938, 75.25228118896484, 74.15727996826172, 17.228092193603516, 20.42828369140625, 71.60816955566406, 11.219268798828125, 45.48982238769531, 12.941740036010742, 27.711532592773438, 29.3043155670166, 48.60061264038086, 21.77667236328125, 24.254911422729492, 45.94057846069336, 20.2563419342041, 21.439178466796875, 63.42179489135742, 15.228118896484375, 17.844221115112305, 11.529494285583496, 66.04071807861328, 8.262402534484863, 10.62664794921875, 67.44671630859375, 16.361312866210938, 26.646581649780273, 12.267983436584473, 62.26682662963867, 16.95305061340332, 25.720853805541992, 42.492767333984375, 20.514022827148438, 46.1982421875, 63.63991165161133, 56.1414794921875, 17.361122131347656, 96.1869125366211, 16.450469970703125, 86.7237319946289, 36.031253814697266, 19.971792221069336, 49.98248291015625, 17.470226287841797, 49.07806396484375, 81.61613464355469, 34.69609451293945, 56.254974365234375, 37.66629409790039, 61.72048568725586, 18.739776611328125, 19.45621109008789, 24.697357177734375, 22.34071159362793, 40.699092864990234, 16.5672607421875, 30.554264068603516, 91.25474548339844, 36.48359680175781, 25.06158447265625, 15.839141845703125, 28.876684188842773, 47.84791946411133, 65.05471801757812, 59.6917724609375, 12.223148345947266, 43.31072998046875, 42.87122344970703, 39.112060546875, 40.17486572265625, 19.5731201171875, 69.70814514160156, 19.02780532836914, 13.997040748596191, 44.86545944213867, 15.164015769958496, 20.24603271484375, 47.92873764038086, 19.61547088623047, 80.767578125, 45.647396087646484, 31.6175537109375, 27.702543258666992, 12.82708740234375, 14.79604434967041, 14.64892578125, 14.81915283203125, 26.473114013671875, 35.982337951660156, 15.5775146484375, 81.29655456542969, 72.362548828125, 52.14392852783203, 14.85588550567627, 23.873483657836914, 20.742431640625, 82.26419830322266, 49.10280990600586, 30.026893615722656, 29.130765914916992, 19.61066436767578, 45.29492950439453, 38.1326904296875, 86.366943359375, 55.563201904296875, 49.957275390625, 53.397674560546875, 32.83546447753906, 29.715578079223633, 30.56671142578125, 16.00640869140625, 19.039215087890625, 63.852821350097656, 54.1474609375, 15.226348876953125, 20.764144897460938, 45.81425857543945, 38.19563293457031, 60.07978820800781, 51.86501693725586, 23.09126853942871, 42.26589584350586, 66.633056640625, 18.977340698242188, 52.555908203125, 17.166677474975586, 29.585058212280273, 59.57624053955078, 66.47994995117188, 16.334449768066406, 29.383590698242188, 25.7650146484375, 20.208419799804688, 25.514373779296875, 30.814666748046875, 72.51934051513672, 36.55043029785156, 12.363922119140625, 17.702316284179688, 130.49832153320312, 10.707305908203125, 12.665419578552246, 53.025691986083984, 34.88662338256836, 23.1627197265625, 62.46868133544922, 74.63563537597656, 63.00318145751953, 1.1711158752441406, 1.2623685598373413, 2.5404253005981445, 1.8943489789962769, 1.8056138753890991, 1.4235994815826416, 2.4571924209594727, 1.6087006330490112, 1.8551092147827148, 1.8303722143173218, 2.351201057434082, 2.0105557441711426, 1.4151982069015503, 2.232198476791382, 1.966395378112793, 2.444578170776367, 2.2220075130462646, 1.5044896602630615, 2.4364938735961914, 1.2989928722381592, 1.8739385604858398, 2.012190341949463, 2.372513771057129, 1.997849702835083, 1.9309395551681519, 2.0791337490081787, 1.7090229988098145, 3.334221363067627, 1.8916540145874023, 2.081757068634033, 1.3337830305099487, 2.796637773513794, 2.2367491722106934, 2.4709856510162354, 2.0621213912963867, 2.939739942550659, 2.9953765869140625, 1.9269083738327026, 2.995234727859497, 2.0709517002105713, 2.012692451477051, 2.2087411880493164, 1.961134910583496, 1.8726435899734497, 2.01822566986084, 1.66759192943573, 1.9824074506759644, 2.0086424350738525, 1.715794324874878, 2.2187788486480713, 1.9616516828536987, 1.5655667781829834, 1.1916608810424805, 2.0742387771606445, 2.370009422302246, 2.138249158859253, 2.2951574325561523, 1.582589864730835, 2.585826873779297, 1.5633269548416138, 2.0773019790649414, 1.8790801763534546, 2.783838987350464, 1.6102265119552612, 1.8038828372955322, 1.9857085943222046, 2.185378074645996, 2.09622859954834, 2.5677332878112793, 2.6059200763702393, 1.056355357170105, 1.5380905866622925, 2.300832509994507, 2.267728567123413, 1.50454843044281, 1.250722050666809, 2.5236825942993164, 2.3223302364349365, 2.4036433696746826, 2.174518585205078, 1.5119733810424805, 1.4867315292358398, 3.3271594047546387, 3.0423388481140137, 2.37026309967041, 1.7926435470581055, 2.0826313495635986, 1.7263039350509644, 1.2068184614181519, 1.9190077781677246, 2.0188255310058594, 3.0038421154022217, 3.320925712585449, 1.336756706237793, 2.856351137161255, 1.1927694082260132, 1.2351179122924805, 2.0725717544555664, 2.397902727127075, 1.2240254878997803, 1.7450166940689087, 1.828888177871704, 2.61226749420166, 2.8606903553009033, 1.9520902633666992, 2.0570592880249023, 1.0545949935913086, 1.7710164785385132, 1.908258318901062, 2.066899538040161, 1.8543126583099365, 2.3292431831359863, 1.0743589401245117, 1.2353183031082153, 2.63602614402771, 2.0897154808044434, 1.5460782051086426, 1.9943413734436035, 2.2982091903686523, 2.330030918121338, 1.714577555656433, 2.7609283924102783, 1.4972048997879028, 1.6813039779663086, 1.6296896934509277, 1.9016408920288086, 2.033778190612793, 2.9471733570098877, 2.117713451385498, 2.41849684715271, 2.568160057067871, 1.5561001300811768, 1.5203622579574585, 1.6970690488815308, 1.9060707092285156, 1.8389081954956055, 2.0330286026000977, 2.661273241043091, 3.103590726852417, 3.4560136795043945, 1.6945922374725342, 1.8619184494018555, 2.9288673400878906, 2.52609920501709, 2.409430503845215, 2.621838331222534, 1.6755715608596802, 1.7452027797698975, 2.760969877243042, 2.387389898300171, 2.229837656021118, 2.6748147010803223, 2.1157453060150146, 2.3357534408569336, 2.4264979362487793, 2.4503374099731445, 1.4214506149291992, 1.48277747631073, 1.3636648654937744, 2.7322096824645996, 1.7649221420288086, 1.8886781930923462, 1.8792427778244019, 1.4460326433181763, 1.4160223007202148, 2.3162755966186523, 2.5232841968536377, 1.8047722578048706, 1.2808713912963867, 1.9219248294830322, 2.187953233718872, 1.9536255598068237, 2.2508974075317383, 2.297919988632202, 2.494640350341797, 1.2815990447998047, 2.419811248779297, 1.8206223249435425, 1.883296012878418, 2.2995147705078125, 2.437279224395752, 1.155928611755371, 1.6530877351760864, 1.7757177352905273, 1.655695915222168, 2.4653918743133545, 1.5183738470077515, 2.6451470851898193, 1.7774180173873901, 2.0609230995178223, 2.4223170280456543, 2.387237071990967, 1.4637014865875244, 2.0691823959350586, 2.1836652755737305, 1.2009267807006836, 1.3883084058761597, 2.1598825454711914, 2.036440134048462, 1.32957923412323, 2.07043194770813, 3.097639799118042, 2.9875710010528564, 1.7708311080932617, 1.9802732467651367, 1.3557767868041992, 2.1615958213806152, 2.5268468856811523, 1.7932026386260986, 2.6263694763183594, 1.620971918106079, 1.7625089883804321, 2.719367027282715, 2.0437841415405273, 1.9029663801193237, 2.49851131439209, 1.4204630851745605, 1.5301200151443481, 1.9809050559997559, 1.8904409408569336, 1.5972776412963867, 2.4867682456970215, 2.62253475189209, 2.2697556018829346, 2.527860403060913, 1.8072926998138428, 1.8403615951538086, 1.721091389656067, 1.4588451385498047, 1.6361724138259888, 1.8522472381591797, 1.9437965154647827, 1.556287407875061, 2.010464668273926, 3.254378080368042, 1.2253493070602417, 1.5649346113204956, 1.4522370100021362, 1.8323827981948853, 1.3978490829467773, 1.6977949142456055, 1.6013201475143433, 1.8281774520874023, 1.4878771305084229, 2.0093183517456055, 1.9903913736343384, 1.4974666833877563, 2.0348329544067383, 1.1538267135620117, 1.5412598848342896, 1.4159307479858398, 2.860555410385132, 2.2315657138824463, 1.2766180038452148, 3.030621290206909, 1.458598256111145, 2.8043107986450195, 1.6401586532592773, 1.7127904891967773, 1.5134819746017456, 2.755046844482422, 0.6707677841186523, 2.5997612476348877, 2.0493249893188477, 2.3211605548858643, 1.755824089050293, 2.234114408493042, 1.8552674055099487, 1.3182668685913086, 1.3969231843948364, 1.9288092851638794, 1.2221955060958862, 3.4402337074279785, 1.5667474269866943, 2.318279504776001, 3.0872223377227783, 1.2798337936401367, 2.224626302719116, 1.1987714767456055, 1.4168472290039062, 1.4024018049240112, 1.0927094221115112, 1.6360349655151367, 1.9445257186889648, 1.859841227531433, 2.798407793045044, 1.225148320198059, 2.5894572734832764, 2.1194849014282227, 2.0951476097106934, 1.652976393699646, 2.1314687728881836, 1.1539772748947144, 1.3338513374328613, 1.8668485879898071, 2.282000780105591, 2.9837467670440674, 1.940885305404663, 2.4883246421813965, 1.1931917667388916, 0.12006471306085587, 0.10976189374923706, 0.08472185581922531, 0.14040575921535492, 0.11103538423776627, 0.07495275139808655, 0.0287095308303833, 0.04542022570967674, 0.08016015589237213, 0.04585176333785057, 0.0732666403055191, 0.1071740984916687, 0.1385004222393036, 0.04697643965482712, 0.14446309208869934, 0.11659790575504303, 0.03838908672332764, 0.07074084877967834, 0.0695115327835083, 0.09943008422851562, 0.05139821767807007, 0.171951562166214, 0.02564864791929722, 0.14049559831619263, 0.05425385758280754, 0.05752290040254593, 0.04270829260349274, 0.13422703742980957, 0.14973114430904388, 0.07322515547275543, 0.04358161240816116, 0.10161792486906052, 0.14733755588531494, 0.12162734568119049, 0.11869459599256516, 0.04224953427910805, 0.08246146887540817, 0.10184335708618164, 0.08151286840438843, 0.07481521368026733, 0.10343640297651291, 0.07208072394132614, 0.151995450258255, 0.04712849482893944, 0.018425825983285904, 0.07160432636737823, 0.055390823632478714, 0.039560526609420776, 0.14982809126377106, 0.10456842184066772, 0.10404319316148758, 0.07230354100465775, 0.10322489589452744, 0.15862566232681274, 0.09195220470428467, 0.05815500020980835, 0.09665988385677338, 0.08749591559171677, 0.10287471860647202, 0.08341150730848312, 0.020318638533353806, 0.039559610188007355, 0.0896795466542244, 0.12333432585000992, 0.12799358367919922, 0.12341916561126709, 0.09387893229722977, 0.11349659413099289, 0.08832758665084839, 0.09173792600631714, 0.14055389165878296, 0.08640627562999725, 0.08606166392564774, 0.06604504585266113, 0.09199641644954681, 0.062265824526548386, 0.05481674149632454, 0.0775105208158493, 0.10954265296459198, 0.09489401429891586, 0.08404320478439331, 0.14755350351333618, 0.12161201238632202, 0.06932597607374191, 0.10165553539991379, 0.07952114939689636, 0.09206300228834152, 0.11634299159049988, 0.09499792009592056, 0.055103421211242676, 0.03894827887415886, 0.11505153030157089, 0.07312030345201492, 0.06364291906356812, 0.012873591855168343, 0.10365527868270874, 0.08838929980993271, 0.12240266799926758, 0.07389110326766968, 0.08232376724481583, 0.11484432220458984, 0.062203194946050644, 0.06877219676971436, 0.07653148472309113, 0.125589057803154, 0.10403446108102798, 0.1410362720489502, 0.0861237496137619, 0.11239653080701828, 0.09103503823280334, 0.1371667981147766, 0.06675844639539719, 0.08681555837392807, 0.11579404771327972, 0.04194341599941254, 0.036200374364852905, 0.0009461527806706727, 0.07631923258304596, 0.09107184410095215, 0.09418006986379623, 0.05539022758603096, 0.11317797750234604, 0.08235214650630951, 0.06542307883501053, 0.09100878238677979, 0.1559150516986847, 0.04341987892985344, 0.0269874706864357, 0.16317227482795715, 0.06480206549167633, 0.08945488929748535, 0.056837353855371475, 0.07518837600946426, 0.10266804695129395, 0.10199817270040512, 0.19984370470046997, 0.05413747578859329, 0.04860634729266167, 0.08262570202350616, 0.023005472496151924, 0.09459465742111206, 0.10629606992006302, 0.10080089420080185, 0.0990237146615982, 0.0361034981906414, 0.09809880703687668, 0.05657888948917389, 0.09449541568756104, 0.1485341191291809, 0.09161420911550522, 0.1261214166879654, 0.08192797750234604, 0.048583872616291046, 0.11674143373966217, 0.07564198970794678, 0.09614301472902298, 0.04824211075901985, 0.09080828726291656, 0.10505697131156921, 0.042171161621809006, 0.07224850356578827, 0.11988630890846252, 0.15714703500270844, 0.13672283291816711, 0.06571270525455475, 0.07146856933832169, 0.1290070116519928, 0.12425316870212555, 0.10642049461603165, 0.09151201695203781, 0.04175765812397003, 0.12198678404092789, 0.048789381980895996, 0.05258893966674805, 0.126151442527771, 0.07292740046977997, 0.10164407640695572, 0.05076265707612038, 0.04254590719938278, 0.04603809118270874, 0.08847818523645401, 0.08800210803747177, 0.030320189893245697, 0.09843812137842178, 0.16353340446949005, 0.08898120373487473, 0.030775470659136772, 0.1748925745487213, 0.11019069701433182, 0.12528616189956665, 0.12462510913610458, 0.16084647178649902, 0.07351333647966385, 0.011143207550048828, 0.062125157564878464, 0.10911858081817627, 0.10293551534414291, 0.03977008908987045, 0.0727527067065239, 0.05457496643066406, 0.11149197071790695, 0.10135263204574585, 0.1416599303483963, 0.0574185773730278, 0.12690819799900055, 0.13408173620700836, 0.0746089518070221, 0.06926161050796509, 0.09852717816829681, 0.08590178936719894, 0.0987364873290062, 0.09737906605005264, 0.10782197117805481, 0.041620977222919464, 0.059489522129297256, 0.09908094257116318, 0.1468677818775177, 0.05084938555955887, 0.03229666128754616, 0.08204822987318039, 0.030246078968048096, 0.11835559457540512, 0.07746583968400955, 0.09399570524692535, 0.09856835752725601, 0.04167475178837776, 0.08629989624023438, 0.06957066059112549, 0.12670442461967468, 0.05144774913787842, 0.11730144172906876, 0.04117116704583168, 0.1139245554804802, 0.11087862402200699, 0.07330131530761719, 0.15618443489074707, 0.1519850343465805, 0.08197120577096939, 0.12791024148464203, 0.07308024168014526, 0.11944892257452011, 0.08656138181686401, 0.09706701338291168, 0.12325829267501831, 0.0434967540204525, 0.13858039677143097, 0.040318068116903305, 0.007801975589245558, 0.18954448401927948, 0.08838479965925217, 0.11060892790555954, 0.11169726401567459, 0.09125100821256638, 0.06352630257606506, 0.10677851736545563, 0.08193068206310272, 0.11876227706670761, 0.08767744153738022, 0.045187558978796005, 0.04541901499032974, 0.04292982816696167, 0.08729516714811325, 0.14472976326942444, 0.07242871820926666, 0.0655265673995018, 0.08640922605991364, 0.1717871129512787, 0.18126265704631805, 0.013495211489498615, 0.08441013097763062, 0.05056814104318619, 0.09033775329589844, 0.09410709142684937, 0.13528209924697876, 0.058603234589099884, 0.09188544750213623, 0.13179072737693787, 0.10311982035636902, 0.06397540122270584, 0.12026973813772202, 0.06507237255573273, 0.09475203603506088, 0.01759236678481102, 0.1332162320613861, 0.09767618775367737, 0.0988847017288208, 0.05623604729771614, 0.18226568400859833, 0.10563674569129944, 0.0694165751338005, 0.13149236142635345, 0.056855570524930954, 0.13373850286006927, 0.151715487241745, 0.017840031534433365, 0.08854719996452332, 0.04531285539269447, 0.09059596061706543, 0.07873672246932983, 0.1221233531832695, 0.814256489276886, 0.6451959013938904, 0.5972397327423096, 0.42677050828933716, 0.19693218171596527, 0.6422064900398254, 0.43666091561317444, 0.5238843560218811, 1.01775324344635, 0.44615989923477173, 0.6965722441673279, 0.6391967535018921, 0.861444890499115, 0.45509010553359985, 0.8065980076789856, 0.5834015011787415, 0.4975976049900055, 0.3723042607307434, 0.46161383390426636, 0.6628901362419128, 0.6303704977035522, 0.7568882703781128, 0.5522009134292603, 0.6194237470626831, 0.3202835023403168, 0.4020400941371918, 0.23973621428012848, 0.7317535281181335, 0.5862762928009033, 0.6404507160186768, 0.3221912980079651, 0.388113409280777, 0.8025339245796204, 0.4043210744857788, 0.47579941153526306, 0.75056391954422, 0.8150442242622375, 0.7844149470329285, 0.5589693188667297, 0.5075894594192505, 1.1672013998031616, 0.753050684928894, 0.5814236402511597, 0.29343080520629883, 0.5687359571456909, 0.5039989948272705, 0.6364803314208984, 0.4995992183685303, 0.5174296498298645, 0.5404613614082336, 0.6322594285011292, 0.6855343580245972, 0.631628155708313, 0.738369882106781, 0.3809424042701721, 0.6236022710800171, 0.5709100365638733, 0.4436257779598236, 0.3088982403278351, 0.359673410654068, 0.6118611097335815, 0.7408451437950134, 0.46387556195259094, 0.33928805589675903, 0.7400990724563599, 0.9088271260261536, 0.25906902551651, 0.31515708565711975, 1.0251957178115845, 0.43584567308425903, 0.5297860503196716, 0.4713233709335327, 0.7655645608901978, 0.664253830909729, 0.7496392130851746, 0.8706246614456177, 0.289595365524292, 0.6782650351524353, 0.47880813479423523, 0.6029980182647705, 0.2867962121963501, 0.4252452850341797, 0.43178993463516235, 0.41809192299842834, 0.8291492462158203, 0.7805651426315308, 0.6022284626960754, 1.0023506879806519, 0.530476450920105, 0.18732337653636932, 0.8357293605804443, 0.4015340805053711, 0.5006240010261536, 1.2053576707839966, 0.2408330887556076, 0.3839811682701111, 0.339116632938385, 0.7461433410644531, 0.5076354146003723, 0.6126311421394348, 0.347252756357193, 0.5384306907653809, 0.9485223889350891, 0.36100754141807556, 0.6275261044502258, 0.652481198310852, 0.4009166657924652, 0.5265909433364868, 0.3447481393814087, 0.4092053472995758, 0.5038135647773743, 0.32300472259521484, 0.21405363082885742, 0.2515692710876465, 0.8643906712532043, 0.25182709097862244, 0.6590835452079773, 0.7368461489677429, 0.6921295523643494, 0.789101243019104, 0.379910409450531, 0.48760947585105896, 0.8068253397941589, 0.5542205572128296, 0.267837792634964, 0.15810227394104004, 0.5069224834442139, 0.3999224901199341, 0.37262430787086487, 0.6612401604652405, 0.6515176296234131, 0.20377376675605774, 0.37848708033561707, 0.4392834007740021, 0.5156561136245728, 0.4149412512779236, 0.488107830286026, 0.3034958243370056, 0.34779056906700134, 1.1214252710342407, 0.8865485191345215, 0.23801864683628082, 0.6399022340774536, 0.6590176820755005, 0.38783225417137146, 0.38246574997901917, 0.9598370790481567, 0.6031157374382019, 0.33350202441215515, 0.8536246418952942, 0.35346952080726624, 0.4549586772918701, 0.8284045457839966, 0.7289407849311829, 0.5568050742149353, 0.11485902220010757, 0.45065680146217346, 0.6081687211990356, 0.7341001629829407, 0.4609586298465729, 0.3666640520095825, 0.539185643196106, 0.4879728853702545, 0.47358351945877075, 0.4711090624332428, 0.8586824536323547, 0.45066893100738525, 0.5878448486328125, 0.4482131004333496, 0.6851289868354797, 0.6636906862258911, 0.4023783802986145, 0.4094633460044861, 0.6322951912879944, 0.3974219858646393, 0.22953979671001434, 0.7006930112838745, 0.6639744639396667, 0.5628775358200073, 0.4818975627422333, 0.511802077293396, 0.9727250337600708, 0.5843315720558167, 0.6247250437736511, 0.8251565098762512, 0.40599822998046875, 0.6830080151557922, 0.8155957460403442, 0.25384747982025146, 0.8172915577888489, 0.6470015645027161, 0.9896014332771301, 0.8430140614509583, 0.5243566036224365, 0.4185207784175873, 0.9091746211051941, 0.8251227140426636, 0.5661799311637878, 0.5053199529647827, 0.35332584381103516, 0.36393752694129944, 0.5898578763008118, 0.7176337242126465, 0.3830161988735199, 0.45275649428367615, 0.6585372090339661, 0.7547607421875, 0.7505390644073486, 0.5787937641143799, 0.3245430588722229, 0.5830329060554504, 0.6223068237304688, 0.2581445872783661, 0.6537642478942871, 0.8266470432281494, 0.3507825434207916, 0.5219606161117554, 0.42596352100372314, 0.7290995717048645, 0.6129589676856995, 0.5706406235694885, 0.5291800498962402, 0.590591311454773, 0.8696752786636353, 0.4690570831298828, 0.3914397358894348, 0.3243052363395691, 0.5100510716438293, 0.4005628228187561, 0.9077050089836121, 0.49328961968421936, 0.9595292210578918, 0.6412423849105835, 0.5884960293769836, 0.7707727551460266, 0.7177255153656006, 0.8592672348022461, 0.8335110545158386, 0.8683826923370361, 0.6924859285354614, 0.4007416367530823, 0.4631809890270233, 0.3477291166782379, 0.7059686779975891, 0.5072030425071716, 0.7035871744155884, 0.41698157787323, 0.6564598083496094, 0.4902949333190918, 0.39855656027793884, 0.42710065841674805, 0.4664955735206604, 0.38635554909706116, 0.5610878467559814, 0.7195532917976379, 0.6130176186561584, 0.7232720255851746, 0.512400209903717, 0.643894612789154, 0.36414635181427, 0.7143850326538086, 0.01043262891471386, 0.7493046522140503, 0.6932528614997864, 0.5316932201385498, 0.20187149941921234, 0.40137892961502075, 0.5872772932052612, 0.5719068646430969, 0.3249130845069885, 0.38277339935302734, 0.33081838488578796, 0.1299070119857788, 0.5078276991844177, 0.7729635238647461, 0.9105389714241028, 0.665064811706543, 0.21251380443572998, 0.5360777974128723, 0.3433029353618622, 1.1982966661453247, 0.5356412529945374, 0.605230987071991, 0.278664231300354, 0.8589637279510498, 0.5267971754074097, 0.4459531307220459, 0.9181258678436279, 0.8287394642829895, 0.5038354396820068, 0.372058242559433, 0.8052864074707031, 0.4870120584964752, 0.5077136754989624, 0.3241044580936432, 0.24943482875823975, 0.9592353701591492, 0.47129499912261963, 0.9425339102745056, 0.4474366307258606, 36.9959716796875, 44.91042709350586, 9.982208251953125, 16.09027862548828, 66.28860473632812, 20.2064208984375, 35.88689041137695, 62.89412307739258, 41.974021911621094, 70.42257690429688, 45.06869888305664, 21.28437614440918, 96.51119232177734, 30.107955932617188, 24.994388580322266, 13.404175758361816, 62.632171630859375, 18.081939697265625, 82.72510528564453, 45.81687545776367, 40.46429443359375, 13.962726593017578, 56.22259521484375, 9.98028564453125, 91.6932601928711, 51.97426223754883, 46.89529037475586, 26.104267120361328, 28.7396240234375, 29.58661460876465, 68.29562377929688, 28.565032958984375, 18.004486083984375, 42.234375, 78.40419006347656, 104.98018646240234, 24.931859970092773, 53.58955764770508, 28.851224899291992, 55.861297607421875, 17.834762573242188, 30.291717529296875, 32.44087219238281, 45.30952835083008, 37.35345458984375, 64.6717529296875, 19.472301483154297, 54.008113861083984, 64.56867218017578, 74.01524353027344, 131.91583251953125, 22.141996383666992, 60.81020736694336, 22.81841278076172, 11.08306884765625, 23.9228515625, 95.44438934326172, 58.594329833984375, 18.297016143798828, 25.213226318359375, 30.36639976501465, 13.661670684814453, 26.82674217224121, 65.32792663574219, 24.162452697753906, 24.431365966796875, 61.27484130859375, 29.56158447265625, 37.81439208984375, 25.368886947631836, 68.72195434570312, 36.880123138427734, 14.17408275604248, 53.20216369628906, 32.78205871582031, 10.343170166015625, 46.66546630859375, 78.42265319824219, 57.94915771484375, 89.65630340576172, 140.0648651123047, 27.52886962890625, 15.520309448242188, 25.613739013671875, 59.83889389038086, 14.300962448120117, 26.302518844604492, 26.11567497253418, 54.64878463745117, 24.505949020385742, 18.638031005859375, 14.720489501953125, 30.77471351623535, 34.366092681884766, 46.33230209350586, 40.554141998291016, 61.53384780883789, 24.613759994506836, 42.7960205078125, 33.428871154785156, 30.600839614868164, 69.47319793701172, 22.525390625, 43.94387435913086, 44.60622787475586, 41.939998626708984, 33.77508544921875, 16.804948806762695, 21.36539077758789, 18.998092651367188, 35.5438232421875, 99.990478515625, 76.89363098144531, 22.83625030517578, 9.806289672851562, 23.359012603759766, 43.16584014892578, 13.220922470092773, 8.70074462890625, 35.30764389038086, 96.49712371826172, 15.293685913085938, 29.74848747253418, 29.700408935546875, 60.10696029663086, 22.33869743347168, 49.35879135131836, 36.692138671875, 34.91357421875, 32.80989074707031, 40.08442687988281, 80.56122589111328, 15.982179641723633, 51.669189453125, 27.085102081298828, 90.78289794921875, 86.11779022216797, 96.07351684570312, 47.5811767578125, 59.84881591796875, 49.862586975097656, 40.13413619995117, 84.57781982421875, 71.35285949707031, 37.62078857421875, 29.133426666259766, 16.15673828125, 37.43595504760742, 26.04534912109375, 26.127830505371094, 45.55340576171875, 30.05146598815918, 58.72601318359375, 33.8416633605957, 41.674686431884766, 69.28509521484375, 50.656707763671875, 101.39727020263672, 34.03139877319336, 12.270691871643066, 74.44756317138672, 13.416229248046875, 132.96051025390625, 42.36360168457031, 34.344940185546875, 13.026580810546875, 43.158939361572266, 16.232038497924805, 123.92931365966797, 15.034852981567383, 54.36474609375, 15.311248779296875, 20.720243453979492, 14.201549530029297, 14.150142669677734, 49.50373458862305, 23.980316162109375, 47.61189651489258, 20.308534622192383, 29.30679702758789, 25.15736198425293, 15.1600341796875, 13.173422813415527, 17.702228546142578, 55.04878234863281, 25.921234130859375, 39.90348815917969, 39.198699951171875, 58.526458740234375, 28.06234359741211, 12.565505027770996, 28.10137939453125, 20.062049865722656, 41.008235931396484, 46.57224655151367, 21.756927490234375, 21.531156539916992, 16.877685546875, 22.119232177734375, 74.00697326660156, 8.56707763671875, 34.70436096191406, 42.34645462036133, 56.9951057434082, 23.637435913085938, 29.429550170898438, 24.23443603515625, 18.22055435180664, 51.118934631347656, 35.67079162597656, 16.11176872253418, 35.6160888671875, 13.551313400268555, 30.780582427978516, 27.10859489440918, 49.49317169189453, 18.02362060546875, 13.992240905761719, 26.49116325378418, 22.363372802734375, 19.85310935974121, 15.207244873046875, 25.239013671875, 88.39419555664062, 17.818119049072266, 37.586761474609375, 31.834012985229492, 42.1603889465332, 20.266918182373047, 18.691837310791016, 52.86916732788086, 74.1769790649414, 38.221256256103516, 22.876678466796875, 23.86409568786621, 48.95122146606445, 63.61685562133789, 68.13162231445312, 27.170761108398438, 57.012996673583984, 87.7123031616211, 114.23504638671875, 16.01189613342285, 47.77410888671875, 16.511444091796875, 99.19283294677734, 25.307830810546875, 115.09271240234375, 17.879650115966797, 61.7498893737793, 58.80145263671875, 25.486812591552734, 13.5435791015625, 54.505428314208984, 23.583480834960938, 25.1632080078125, 61.02426528930664, 17.450836181640625, 25.2813720703125, 53.126522064208984, 19.924053192138672, 22.303680419921875, 15.592453002929688, 41.061981201171875, 31.151029586791992, 20.442405700683594, 14.07550048828125, 23.545194625854492, 28.25601577758789, 62.35908508300781, 93.06900024414062, 76.56818389892578, 15.679020881652832, 34.552093505859375, 13.369747161865234, 40.10696029663086, 27.867460250854492, 15.997580528259277, 57.98659896850586, 15.604217529296875, 13.207258224487305, 25.81074333190918, 61.21820068359375, 51.3939208984375, 92.1400146484375, 19.617706298828125, 15.037200927734375, 37.22194290161133, 32.43654251098633, 26.10302734375, 82.84093475341797, 90.02755737304688, 51.82469940185547, 79.90139770507812, 33.18178939819336, 17.936004638671875, 69.69284057617188, 50.97184371948242, 21.75178337097168, 27.602121353149414, 2.541447639465332, 3.036242723464966, 1.503620982170105, 2.4873673915863037, 1.923592448234558, 2.96197247505188, 2.6140990257263184, 1.413041353225708, 1.987475872039795, 2.982635498046875, 2.314558982849121, 2.2382211685180664, 1.6101739406585693, 2.5042967796325684, 2.308927297592163, 1.3313207626342773, 1.3536796569824219, 2.7186501026153564, 1.5736913681030273, 3.1761279106140137, 1.7122875452041626, 2.017697334289551, 1.9428831338882446, 1.2892262935638428, 1.3770170211791992, 1.9422698020935059, 1.9758939743041992, 2.2550606727600098, 1.2565040588378906, 2.1403005123138428, 2.138840913772583, 1.8966301679611206, 1.5798348188400269, 2.4032721519470215, 1.0592056512832642, 2.712968111038208, 2.6951873302459717, 1.3803510665893555, 2.311453104019165, 2.7748730182647705, 1.765339732170105, 2.9965014457702637, 1.895590901374817, 1.8745031356811523, 2.4831786155700684, 2.077925443649292, 2.94107723236084, 3.099787473678589, 2.729945659637451, 1.7583669424057007, 2.282210350036621, 2.406869411468506, 4.036298751831055, 1.0941637754440308, 1.4361333847045898, 1.9694933891296387, 3.360992908477783, 1.3141144514083862, 1.8157591819763184, 2.3497250080108643, 2.874202251434326, 1.6067585945129395, 2.1331052780151367, 1.4226675033569336, 1.4881948232650757, 2.495617628097534, 2.1277289390563965, 1.6388393640518188, 1.4960471391677856, 1.556251049041748, 2.3695459365844727, 2.65059494972229, 2.2690038681030273, 2.2127418518066406, 2.660583019256592, 1.6128780841827393, 2.0791759490966797, 3.177500009536743, 2.229841470718384, 1.0965557098388672, 3.021651029586792, 2.2339468002319336, 2.2720298767089844, 1.7548388242721558, 2.4843807220458984, 1.441398024559021, 1.4773168563842773, 1.7096368074417114, 2.5788629055023193, 2.4256927967071533, 1.9723119735717773, 1.461018443107605, 2.2552711963653564, 0.741646945476532, 2.2627792358398438, 1.0484451055526733, 1.9491524696350098, 2.336270570755005, 1.8241225481033325, 2.7925522327423096, 2.501225471496582, 1.786097526550293, 2.6783523559570312, 1.5793946981430054, 1.4957069158554077, 2.0030910968780518, 1.269218921661377, 2.8504626750946045, 1.932464838027954, 3.724043846130371, 2.2898170948028564, 1.6078847646713257, 1.9286507368087769, 3.0544304847717285, 3.190790891647339, 2.5885367393493652, 2.5479116439819336, 1.7647253274917603, 2.332167625427246, 1.402374505996704, 2.251601457595825, 1.7499440908432007, 2.6249115467071533, 2.9043986797332764, 1.6060781478881836, 2.61252498626709, 1.7234925031661987, 1.9689650535583496, 3.0942420959472656, 1.5962045192718506, 2.207909107208252, 1.6665276288986206, 2.125210762023926, 2.3737175464630127, 2.200106143951416, 1.14280366897583, 2.042789936065674, 1.4424200057983398, 1.602070689201355, 2.781691789627075, 2.9443256855010986, 2.395017147064209, 1.1017807722091675, 1.654061198234558, 2.6376891136169434, 1.410172700881958, 1.760609745979309, 2.282742500305176, 2.6100566387176514, 1.7157217264175415, 1.6849355697631836, 3.0620086193084717, 1.7310014963150024, 1.3475338220596313, 2.439521312713623, 2.712754487991333, 1.9630370140075684, 2.127781867980957, 2.7125887870788574, 1.323634147644043, 2.104259490966797, 2.382073402404785, 1.5080785751342773, 3.160099983215332, 1.9551811218261719, 2.1315927505493164, 2.10837459564209, 2.9235241413116455, 2.4325575828552246, 1.9806225299835205, 2.333500862121582, 2.1443631649017334, 1.4775742292404175, 1.1166744232177734, 2.650425910949707, 1.960984468460083, 1.76506507396698, 2.1954152584075928, 1.91545832157135, 2.07934832572937, 2.150639533996582, 1.7917145490646362, 2.251664161682129, 2.3559999465942383, 0.8918294906616211, 1.7944974899291992, 2.375065803527832, 2.514625072479248, 2.3742802143096924, 2.484426736831665, 1.5325274467468262, 3.387502431869507, 1.0433422327041626, 1.321681022644043, 3.006010055541992, 1.992867112159729, 2.7756078243255615, 1.3206833600997925, 2.0345184803009033, 2.1443512439727783, 2.343506336212158, 1.485634684562683, 1.8817930221557617, 2.1616430282592773, 1.9999505281448364, 2.040475606918335, 2.54909610748291, 1.496423602104187, 1.689069151878357, 2.8225696086883545, 1.8013944625854492, 2.4940474033355713, 1.8171929121017456, 3.0010693073272705, 1.793048620223999, 1.9132895469665527, 1.9525856971740723, 1.2189207077026367, 1.882676362991333, 1.5995644330978394, 2.4226391315460205, 2.5715231895446777, 2.174635887145996, 1.698364496231079, 2.3741769790649414, 1.550911784172058, 2.0811777114868164, 3.2247233390808105, 1.7063031196594238, 2.5651626586914062, 1.4443082809448242, 1.2191170454025269, 1.553227186203003, 2.745539426803589, 2.091651678085327, 2.1669092178344727, 1.867732048034668, 1.4519692659378052, 2.092841148376465, 1.4665005207061768, 1.3828580379486084, 2.5184924602508545, 2.4171695709228516, 2.3780813217163086, 1.6121370792388916, 1.5307930707931519, 3.468766450881958, 2.3479092121124268, 1.365043044090271, 1.568718671798706, 1.965266227722168, 1.8642946481704712, 2.275972604751587, 2.607386350631714, 2.1775569915771484, 1.7944787740707397, 2.1519501209259033, 2.404393196105957, 1.943924069404602, 1.221596360206604, 2.62689208984375, 2.981710195541382, 2.3901796340942383, 1.6996184587478638, 1.656413197517395, 1.5959112644195557, 2.2937536239624023, 1.7660350799560547, 2.372788429260254, 2.544872283935547, 2.7720253467559814, 2.092430353164673, 2.9110522270202637, 3.081700325012207, 2.5226728916168213, 1.7108335494995117, 1.8035629987716675, 3.0679712295532227, 1.5625582933425903, 2.8114044666290283, 1.421579360961914, 2.2099263668060303, 1.331822156906128, 1.7520947456359863, 1.4750131368637085, 2.0104150772094727, 2.1557347774505615, 1.1822986602783203, 2.7637791633605957, 1.9630554914474487, 2.384274482727051, 1.22722327709198, 2.190460205078125, 2.144202470779419, 2.7550270557403564, 2.010469913482666, 3.4883265495300293, 1.696539282798767, 1.8078539371490479, 1.907454490661621, 0.08175604045391083, 0.11457448452711105, 0.12819865345954895, 0.10629798471927643, 0.10169143229722977, 0.021778855472803116, 0.06590509414672852, 0.08872747421264648, 0.06511934101581573, 0.06100987270474434, 0.09845506399869919, 0.12386773526668549, 0.12331339716911316, 0.15662071108818054, 0.06882000714540482, 0.04681754112243652, 0.1696840077638626, 0.13924723863601685, 0.0676916167140007, 0.09336802363395691, 0.13616906106472015, 0.07712242752313614, 0.1885775774717331, 0.08505941182374954, 0.07316164672374725, 0.09465490281581879, 0.16048693656921387, 0.1648268699645996, 0.09570484608411789, 0.06671620905399323, 0.055697839707136154, 0.0662480816245079, 0.08923003077507019, 0.07439928501844406, 0.09054822474718094, 0.08861906826496124, 0.07439150661230087, 0.06903970241546631, 0.09111664444208145, 0.11435931921005249, 0.05591748654842377, 0.08513164520263672, 0.108942411839962, 0.05224839970469475, 0.1267893761396408, 0.13269753754138947, 0.10108672827482224, 0.178558349609375, 0.08958666771650314, 0.05766952037811279, 0.0759272351861, 0.04324854165315628, 0.10525476187467575, 0.12000333517789841, 0.02584400586783886, 0.03829532861709595, 0.0586429201066494, 0.07773258537054062, 0.08021879196166992, 0.08466439694166183, 0.1351783126592636, 0.1242915540933609, 0.11539936065673828, 0.07689633965492249, 0.05166430398821831, 0.13679350912570953, 0.07482068985700607, 0.10606460273265839, 0.08752849698066711, 0.09668563306331635, 0.08066503703594208, 0.06315894424915314, 0.11681472510099411, 0.07887975871562958, 0.11789506673812866, 0.112922303378582, 0.071532242000103, 0.025467557832598686, 0.104988232254982, 0.01919955015182495, 0.07412633299827576, 0.03142335265874863, 0.060841940343379974, 0.08379603922367096, 0.097240149974823, 0.1167336255311966, 0.09730374068021774, 0.047475576400756836, 0.15847247838974, 0.10370542109012604, 0.051437195390462875, 0.17887282371520996, 0.16691656410694122, 0.17073678970336914, 0.07012145221233368, 0.1339409202337265, 0.08512528240680695, 0.1064518541097641, 0.08581900596618652, 0.018461834639310837, 0.10869544744491577, 0.11295000463724136, 0.07663511484861374, 0.1654580682516098, 0.13460755348205566, 0.15313537418842316, 0.1222076416015625, 0.10764443874359131, 0.09310870617628098, 0.06214895471930504, 0.07168543338775635, 0.08075344562530518, 0.09868288040161133, 0.11243817955255508, 0.057293184101581573, 0.05496126413345337, 0.08051248639822006, 0.11859935522079468, 0.03440210223197937, 0.07320734113454819, 0.07476147264242172, 0.09036653488874435, 0.08663596212863922, 0.056217923760414124, 0.12454918771982193, 0.06527835875749588, 0.059320610016584396, 0.09180588275194168, 0.061544954776763916, 0.04391175135970116, 0.028921371325850487, 0.1431044340133667, 0.13572770357131958, 0.051618754863739014, 0.17479228973388672, 0.16901543736457825, 0.08238077163696289, 0.07689478993415833, 0.08592748641967773, 0.05291295051574707, 0.07742688804864883, 0.10041636228561401, 0.09309720993041992, 0.1096997782588005, 0.10346293449401855, 0.07454151660203934, 0.06955963373184204, 0.044598616659641266, 0.11843482404947281, 0.15595237910747528, 0.075166255235672, 0.05900515243411064, 0.08331501483917236, 0.02214975841343403, 0.09274649620056152, 0.05665307864546776, 0.04874258115887642, 0.07628925889730453, 0.06327138841152191, 0.11095888912677765, 0.0860775038599968, 0.06438577175140381, 0.1130189299583435, 0.16516032814979553, 0.10549663007259369, 0.06241555139422417, 0.1858970820903778, 0.17205308377742767, 0.04025440290570259, 0.11445564031600952, 0.08001470565795898, 0.07434923201799393, 0.0536157600581646, 0.10826043784618378, 0.02664012834429741, 0.13803543150424957, 0.02312128059566021, 0.076710045337677, 0.035020530223846436, 0.10600139200687408, 0.008957624435424805, 0.12826846539974213, 0.1572006791830063, 0.07742740213871002, 0.05635758116841316, 0.125444233417511, 0.03322068229317665, 0.08882848173379898, 0.12141986936330795, 0.06368069350719452, 0.10106592625379562, 0.09070726484060287, 0.09085126966238022, 0.06732845306396484, 0.12673765420913696, 0.09596119076013565, 0.06643068045377731, 0.046358622610569, 0.0764816403388977, 0.13919322192668915, 0.08524885773658752, 0.09807033091783524, 0.12800653278827667, 0.05828279256820679, 0.019871532917022705, 0.11834301799535751, 0.08622784167528152, 0.05835891515016556, 0.07175329327583313, 0.09877049922943115, 0.025355147197842598, 0.058037858456373215, 0.0806366354227066, 0.061285536736249924, 0.06450463831424713, 0.040361881256103516, 0.07979172468185425, 0.09281598776578903, 0.10078679770231247, 0.12041379511356354, 0.08771927654743195, 0.054352767765522, 0.19111838936805725, 0.09842151403427124, 0.04425877332687378, 0.1293056309223175, 0.09688884764909744, 0.08613184839487076, 0.050789784640073776, 0.0719214454293251, 0.1113615557551384, 0.15509623289108276, 0.03427381068468094, 0.08018157631158829, 0.07553376257419586, 0.09439880400896072, 0.10951995849609375, 0.1506759375333786, 0.08423352241516113, 0.06601560115814209, 0.061416205018758774, 0.043507449328899384, 0.12007064372301102, 0.0726374164223671, 0.13506543636322021, 0.04603952169418335, 0.03125704079866409, 0.0726199671626091, 0.07612008601427078, 0.06166303530335426, 0.07880108803510666, 0.10225919634103775, 0.08717504143714905, 0.1414451003074646, 0.08301448822021484, 0.06691481173038483, 0.09747079759836197, 0.20256948471069336, 0.06229880079627037, 0.10956171154975891, 0.0879136249423027, 0.05793028697371483, 0.11025245487689972, 0.11192011833190918, 0.015752019360661507, 0.09708190709352493, 0.06848102062940598, 0.17715713381767273, 0.13001254200935364, 0.15170860290527344, 0.04232092946767807, 0.08352264016866684, 0.05013667792081833, 0.11865357309579849, 0.1288852095603943, 0.1635289192199707, 0.10879257321357727, 0.08777330070734024, 0.07801966369152069, 0.0832676887512207, 0.03454191982746124, 0.10563309490680695, 0.020904049277305603, 0.09162870049476624, 0.10921312123537064, 0.08847397565841675, 0.06637066602706909, 0.044345177710056305, 0.06323361396789551, 0.09585017710924149, 0.10782849788665771, 0.011701628565788269, 0.08150220662355423, 0.08600848913192749, 0.14046922326087952, 0.10581721365451813, 0.05352502688765526, 0.11858992278575897, 0.06501878798007965, 0.08059802651405334, 0.34826087951660156, 0.528976559638977, 0.43192926049232483, 1.0473138093948364, 0.29752424359321594, 0.48007529973983765, 0.6126426458358765, 0.9247744679450989, 0.9910652041435242, 0.5483336448669434, 0.38950639963150024, 0.9901658296585083, 0.8747302293777466, 0.642932116985321, 0.5672586560249329, 0.32695600390434265, 0.7306382060050964, 0.6270185708999634, 0.6265116333961487, 1.1758239269256592, 0.29491308331489563, 0.7276555299758911, 0.33446547389030457, 0.7088230848312378, 0.531791090965271, 0.42801225185394287, 0.3951058089733124, 0.45929843187332153, 0.675749659538269, 0.5607627034187317, 0.7049683928489685, 0.26870763301849365, 0.4317456781864166, 0.6747488379478455, 0.3358364701271057, 0.17650501430034637, 0.5495864152908325, 0.5472995042800903, 0.8190078735351562, 0.437019020318985, 0.5585367679595947, 0.6841885447502136, 0.5799040794372559, 0.7011286616325378, 0.5840917229652405, 0.5043962597846985, 0.5278720855712891, 0.612677276134491, 0.5482649803161621, 0.6349296569824219, 0.48346295952796936, 0.2653466463088989, 0.5350630879402161, 0.5146453380584717, 0.4346188008785248, 0.2593117952346802, 0.3977300822734833, 0.5459694266319275, 0.42839446663856506, 0.6559762358665466, 0.6743862628936768, 0.24441905319690704, 0.5472225546836853, 0.6658665537834167, 0.4955390691757202, 0.35842424631118774, 0.6081010103225708, 0.3491854667663574, 0.409707635641098, 0.6992209553718567, 0.4586150348186493, 0.5493740439414978, 0.9590958952903748, 0.7956272959709167, 0.6996290683746338, 0.7982524037361145, 0.19341881573200226, 0.29158294200897217, 0.3789900839328766, 0.6751624941825867, 1.0752063989639282, 0.49989721179008484, 0.5743013620376587, 0.5673369765281677, 0.5013840198516846, 0.3086993098258972, 0.3158102035522461, 0.5190764665603638, 0.8052886128425598, 0.40165770053863525, 0.5931094884872437, 0.593883216381073, 0.7052626609802246, 0.9819083213806152, 0.8882688879966736, 0.4542315602302551, 0.9418185353279114, 0.48262929916381836, 0.6261926293373108, 0.4421095848083496, 0.29588595032691956, 1.1037304401397705, 0.24113720655441284, 0.5584002733230591, 0.5677359700202942, 0.3317355215549469, 0.44181594252586365, 0.888788640499115, 0.707770824432373, 0.40274864435195923, 0.6584486961364746, 0.5834174752235413, 0.4591643810272217, 0.6676087975502014, 0.4729560613632202, 0.43225374817848206, 0.6118836998939514, 0.6916053891181946, 0.42106786370277405, 0.5089778900146484, 0.9938594698905945, 0.7037872672080994, 0.44713106751441956, 0.6383470296859741, 0.6354361772537231, 0.26536494493484497, 0.5579299926757812, 1.0116537809371948, 0.44281482696533203, 0.25139471888542175, 0.6411245465278625, 0.7960880994796753, 0.5615134835243225, 0.3749757409095764, 0.2422429621219635, 0.27761176228523254, 0.8204138875007629, 0.9058138728141785, 0.8232961893081665, 0.19039495289325714, 0.18316161632537842, 0.48092886805534363, 0.30692991614341736, 0.9860007762908936, 0.41874960064888, 0.8259173631668091, 0.5866991281509399, 0.28336474299430847, 0.38282203674316406, 0.5187597274780273, 0.8625128269195557, 0.24570636451244354, 0.3708198070526123, 0.29130247235298157, 0.8975794315338135, 0.8983175754547119, 0.567893922328949, 0.8568389415740967, 0.4766697585582733, 0.636184811592102, 0.8661257028579712, 0.6056048274040222, 0.5404837727546692, 0.24967128038406372, 0.8723794221878052, 0.6679405570030212, 0.43999457359313965, 0.9458000063896179, 0.5516980886459351, 0.8978447318077087, 0.555822491645813, 0.4156588613986969, 0.6864175200462341, 0.6005069017410278, 0.5266169905662537, 0.6619304418563843, 0.6220095157623291, 0.7322832942008972, 0.8014559745788574, 0.23313041031360626, 0.7099238634109497, 0.57425856590271, 0.5268560647964478, 0.28145745396614075, 0.19078008830547333, 0.2873217463493347, 0.570798933506012, 0.505680501461029, 0.8392395377159119, 0.6896265149116516, 0.38846397399902344, 0.8172172904014587, 0.8497849702835083, 0.4788285791873932, 0.4739550054073334, 0.4647041857242584, 0.39786258339881897, 0.428729385137558, 0.5983976125717163, 0.8758129477500916, 0.5077201128005981, 0.4174593389034271, 0.9552466869354248, 0.5474236607551575, 0.5881391763687134, 0.6287229657173157, 0.3578449785709381, 0.5756110548973083, 0.49069666862487793, 0.6543354392051697, 0.5395854711532593, 0.8462732434272766, 1.2056238651275635, 0.5473403930664062, 0.17386634647846222, 0.4575830101966858, 0.5699983835220337, 0.5512226819992065, 0.558081865310669, 0.5557550191879272, 0.9990177154541016, 0.44244319200515747, 0.6815983653068542, 0.5509351491928101, 0.4291198253631592, 0.30529680848121643, 0.6906605958938599, 0.8964436054229736, 1.0821417570114136, 0.4041064977645874, 0.6076920032501221, 0.6896883249282837, 0.22413577139377594, 0.4865051209926605, 0.6204096674919128, 0.3759130835533142, 0.7059535980224609, 0.5142863392829895, 0.42166656255722046, 0.44809356331825256, 0.6927329897880554, 0.7418131828308105, 0.6659632921218872, 0.9516280293464661, 0.9188075065612793, 0.49673181772232056, 0.8842739462852478, 0.6870226860046387, 0.3488980829715729, 0.2770634889602661, 0.37486228346824646, 0.18049198389053345, 0.5387848615646362, 0.22345802187919617, 0.5118641257286072, 0.4771946370601654, 0.6182190775871277, 0.43763357400894165, 0.3356039226055145, 0.4688970148563385, 0.5587791204452515, 0.3117824196815491, 0.5100271701812744, 0.4761883318424225, 0.4443793296813965, 0.6642419099807739, 0.9353482127189636, 0.8726308941841125, 0.8061680197715759, 0.5535367131233215, 0.9484308362007141, 0.4659319519996643, 0.5457804799079895, 0.5706772208213806, 0.26027584075927734, 0.8309901356697083, 0.3963549733161926, 0.5014574527740479, 0.8977186679840088, 0.8285622000694275, 0.783115804195404, 0.6732503175735474, 0.30299684405326843, 0.9829810261726379, 0.7414757609367371, 0.17367048561573029, 0.6344175934791565, 0.3792952597141266, 0.20270705223083496, 0.5325403809547424, 1.0042644739151, 0.7086389660835266, 0.6728898286819458, 0.5406777262687683, 0.5481045842170715, 0.6836084127426147, 0.4727744162082672, 0.311970055103302, 0.60447758436203, 0.36614513397216797, 19.964599609375, 47.15741729736328, 19.998382568359375, 51.87928771972656, 22.86907958984375, 19.723724365234375, 65.17800903320312, 14.248222351074219, 46.15176010131836, 49.999725341796875, 20.769256591796875, 90.82677459716797, 57.44938278198242, 66.34695434570312, 62.582035064697266, 28.047836303710938, 43.945274353027344, 19.728485107421875, 38.1657600402832, 100.1626968383789, 77.888671875, 79.47197723388672, 16.77203941345215, 84.67987060546875, 22.774993896484375, 115.78872680664062, 28.73095703125, 14.599700927734375, 73.15459442138672, 17.34954833984375, 15.827056884765625, 77.69060516357422, 25.96551513671875, 30.687240600585938, 23.812152862548828, 22.660614013671875, 20.48805046081543, 74.13726043701172, 31.160945892333984, 64.30785369873047, 84.74769592285156, 101.2030258178711, 19.601470947265625, 106.90010833740234, 72.53529357910156, 82.99392700195312, 69.95623779296875, 59.418861389160156, 50.71014404296875, 55.96269226074219, 62.13491439819336, 44.27700424194336, 36.06142807006836, 38.14358139038086, 59.3908576965332, 40.46424102783203, 45.97848892211914, 32.168914794921875, 34.35496520996094, 15.594788551330566, 129.809814453125, 49.370819091796875, 57.18772506713867, 21.953109741210938, 20.358108520507812, 17.942413330078125, 62.82412338256836, 50.99485397338867, 48.75776290893555, 18.426652908325195, 38.2069091796875, 25.808109283447266, 48.39493179321289, 14.232258796691895, 25.58991813659668, 57.67877197265625, 38.29742431640625, 113.29794311523438, 37.84014892578125, 59.40969467163086, 49.35101318359375, 16.066423416137695, 27.04339599609375, 17.866973876953125, 67.09784698486328, 51.5274658203125, 37.11515426635742, 76.9639892578125, 79.62225341796875, 42.9726448059082, 46.62371826171875, 34.76613998413086, 57.33485794067383, 20.60267448425293, 14.64849853515625, 23.429656982421875, 34.6922492980957, 73.229736328125, 46.183162689208984, 39.073368072509766, 41.2413330078125, 13.339313507080078, 12.1773681640625, 56.70621871948242, 19.18505859375, 82.09786987304688, 42.8966064453125, 80.11305236816406, 16.993953704833984, 79.55207824707031, 18.559783935546875, 39.241111755371094, 21.89215087890625, 26.038724899291992, 53.70459747314453, 50.1345100402832, 28.25672721862793, 54.12953186035156, 36.4633903503418, 65.92904663085938, 54.61363220214844, 12.66461181640625, 26.094438552856445, 59.278656005859375, 58.13086700439453, 21.80902099609375, 39.595035552978516, 18.749725341796875, 33.775146484375, 21.730688095092773, 32.1428108215332, 45.51985549926758, 66.83612823486328, 43.668914794921875, 58.9181022644043, 24.010873794555664, 86.60856628417969, 50.745330810546875, 23.763839721679688, 28.350250244140625, 43.786190032958984, 88.79670715332031, 58.991546630859375, 83.3741226196289, 20.486801147460938, 28.333290100097656, 32.14933776855469, 44.26985168457031, 40.24406814575195, 77.9186782836914, 127.33856201171875, 30.125070571899414, 30.388944625854492, 17.597076416015625, 61.4541015625, 44.86733627319336, 44.39081573486328, 30.377347946166992, 16.79224395751953, 28.462543487548828, 72.96723175048828, 58.17401123046875, 30.35633659362793, 53.03237533569336, 17.420148849487305, 67.98745727539062, 51.41755676269531, 58.273284912109375, 27.35400390625, 50.26685333251953, 17.177515029907227, 14.470768928527832, 62.47052001953125, 14.286364555358887, 38.90134048461914, 113.70845794677734, 20.589258193969727, 19.09259796142578, 61.60427474975586, 52.93300247192383, 91.04071044921875, 61.4154167175293, 29.476669311523438, 30.481468200683594, 35.21815872192383, 98.4366226196289, 51.06666946411133, 29.08648681640625, 60.67543411254883, 11.869402885437012, 106.54217529296875, 53.8621826171875, 35.16822814941406, 49.25893783569336, 42.60952377319336, 100.09366607666016, 118.89092254638672, 81.22630310058594, 122.14764404296875, 11.595949172973633, 25.223146438598633, 38.50311279296875, 61.988826751708984, 30.436004638671875, 11.995994567871094, 39.31781005859375, 27.542587280273438, 58.08055877685547, 80.36880493164062, 27.653566360473633, 45.177978515625, 24.20869255065918, 19.78045654296875, 13.965587615966797, 40.624698638916016, 18.996932983398438, 93.54317474365234, 78.43443298339844, 28.442167282104492, 51.735443115234375, 62.650936126708984, 115.698974609375, 29.370731353759766, 125.5164794921875, 38.955482482910156, 88.86769104003906, 17.505146026611328, 13.808258056640625, 49.2198486328125, 52.274139404296875, 52.87307357788086, 46.11442184448242, 15.469451904296875, 22.786956787109375, 29.95203971862793, 14.267298698425293, 36.63999938964844, 54.403358459472656, 17.030855178833008, 21.87286376953125, 21.405685424804688, 33.77043151855469, 60.81611251831055, 42.6622314453125, 20.230712890625, 16.48687744140625, 10.08258056640625, 38.895835876464844, 24.40159797668457, 46.855560302734375, 19.62873077392578, 126.9125747680664, 47.97954177856445, 147.5939178466797, 114.21408081054688, 19.461727142333984, 38.87066650390625, 98.1947250366211, 63.217098236083984, 29.96823501586914, 42.110565185546875, 22.511991500854492, 59.221107482910156, 71.08883666992188, 48.35786056518555, 48.27265167236328, 16.173858642578125, 45.56716537475586, 29.140932083129883, 35.20277404785156, 14.678558349609375, 53.07954788208008, 74.03705596923828, 24.874662399291992, 29.424030303955078, 14.244369506835938, 55.71826934814453, 17.99799919128418, 18.61101722717285, 29.810453414916992, 20.654325485229492, 28.509037017822266, 17.41741943359375, 27.70204734802246, 64.40042114257812, 74.646728515625, 55.09564208984375, 36.396728515625, 32.687835693359375, 14.356964111328125, 29.213104248046875, 39.64649963378906, 17.927974700927734, 101.79782104492188, 89.97804260253906, 46.361572265625, 111.14729309082031, 98.36431121826172, 32.35986328125, 87.295166015625, 1.64616858959198, 1.2036789655685425, 2.976158380508423, 0.9890432357788086, 1.7124509811401367, 2.4755570888519287, 2.154080390930176, 2.160822868347168, 1.9276665449142456, 1.4856524467468262, 1.862751841545105, 2.190821886062622, 2.429205894470215, 2.4086101055145264, 1.8793401718139648, 2.2123546600341797, 1.7215684652328491, 2.641556978225708, 3.882845878601074, 2.7652862071990967, 1.4740188121795654, 1.325019359588623, 1.8171871900558472, 1.432106852531433, 2.6173086166381836, 1.641049861907959, 2.4011943340301514, 2.3080265522003174, 1.1221730709075928, 2.465249538421631, 1.5722817182540894, 2.2523374557495117, 2.4284799098968506, 2.5614659786224365, 1.6726555824279785, 3.060556650161743, 2.670275926589966, 1.8308134078979492, 1.7439374923706055, 1.7173165082931519, 1.9757180213928223, 0.9990777373313904, 2.207463502883911, 1.5558958053588867, 1.9607900381088257, 1.5230779647827148, 2.5823800563812256, 2.2743752002716064, 1.1481895446777344, 1.238976240158081, 2.351834774017334, 1.536599040031433, 3.24788498878479, 2.2968225479125977, 1.9538146257400513, 2.1394872665405273, 2.3544609546661377, 1.5740958452224731, 1.4687241315841675, 2.4168455600738525, 2.557715654373169, 2.1157960891723633, 1.8325445652008057, 2.1525521278381348, 2.158926248550415, 1.2430733442306519, 1.4916008710861206, 1.597792625427246, 2.8621933460235596, 2.695032835006714, 1.3225878477096558, 1.2441834211349487, 2.5973401069641113, 1.7660415172576904, 1.600214958190918, 2.589672803878784, 1.8358107805252075, 1.401940941810608, 1.8469161987304688, 1.860005497932434, 2.625540018081665, 2.610576629638672, 2.133826971054077, 1.5355852842330933, 2.0385921001434326, 1.9484511613845825, 1.5824346542358398, 1.811787486076355, 2.082526206970215, 1.3004119396209717, 2.911655902862549, 2.768782615661621, 3.0737712383270264, 2.491974115371704, 2.1418466567993164, 2.517571449279785, 1.383040428161621, 2.764117479324341, 2.696012020111084, 2.3905839920043945, 2.00460147857666, 1.7937982082366943, 1.668665885925293, 2.185336112976074, 1.8402481079101562, 2.4911279678344727, 2.0015807151794434, 2.0283708572387695, 2.386854648590088, 1.6596802473068237, 1.083287239074707, 2.7622101306915283, 2.097705602645874, 2.579437255859375, 1.7776888608932495, 1.8968762159347534, 1.4816961288452148, 2.690422534942627, 2.3546886444091797, 1.5573078393936157, 3.2866451740264893, 1.2757543325424194, 2.69387149810791, 1.5540828704833984, 1.8113393783569336, 1.662543773651123, 1.2971105575561523, 1.4782682657241821, 2.643284320831299, 1.991499900817871, 1.8450020551681519, 2.3287878036499023, 2.340508460998535, 1.2679587602615356, 3.0080156326293945, 2.663782835006714, 2.205716609954834, 2.838425874710083, 2.907013416290283, 1.7971709966659546, 2.268113136291504, 2.384622097015381, 1.4817818403244019, 2.1911377906799316, 2.5201926231384277, 2.611010789871216, 2.981417179107666, 1.8158483505249023, 2.441516637802124, 1.7309279441833496, 2.171281099319458, 1.2306013107299805, 2.6153838634490967, 1.4388647079467773, 1.667703628540039, 1.4347432851791382, 2.22385573387146, 2.7103111743927, 2.8367631435394287, 1.8405184745788574, 3.2770659923553467, 1.608125925064087, 1.2795761823654175, 1.7562326192855835, 2.3779094219207764, 2.3143022060394287, 2.0807411670684814, 2.4388513565063477, 2.8723254203796387, 3.6126646995544434, 1.6941938400268555, 2.670863389968872, 2.5821807384490967, 1.4431829452514648, 2.4200403690338135, 1.5002012252807617, 1.4378389120101929, 2.0548644065856934, 2.3016624450683594, 2.144829511642456, 1.9539544582366943, 2.1699702739715576, 1.4410370588302612, 2.6327409744262695, 2.9040162563323975, 1.7044553756713867, 2.4148340225219727, 2.0191502571105957, 2.2281432151794434, 2.410006284713745, 3.036616563796997, 2.2480878829956055, 1.572657585144043, 2.705214262008667, 2.847400188446045, 1.8774231672286987, 1.146005630493164, 2.3964757919311523, 1.33733332157135, 3.034074068069458, 1.7661330699920654, 2.2002689838409424, 1.7168930768966675, 1.8024755716323853, 1.9314196109771729, 2.228238582611084, 2.902000665664673, 1.912392258644104, 2.6192424297332764, 1.8863805532455444, 2.3949575424194336, 2.1015565395355225, 2.4550750255584717, 2.5654730796813965, 1.4522980451583862, 2.6325063705444336, 1.4160088300704956, 1.373214840888977, 1.5262653827667236, 1.8310832977294922, 1.3013973236083984, 2.4734737873077393, 2.1814630031585693, 1.567683219909668, 1.487910270690918, 1.7528752088546753, 1.86272132396698, 3.1059820652008057, 1.791245698928833, 2.1713132858276367, 1.7420287132263184, 2.053929328918457, 1.809407114982605, 3.455918550491333, 1.5889252424240112, 2.8778491020202637, 1.6028450727462769, 3.126370668411255, 1.5615568161010742, 1.587518334388733, 1.5085502862930298, 1.8426302671432495, 2.878566026687622, 1.5896406173706055, 1.6117430925369263, 2.6645684242248535, 1.728053092956543, 2.647091865539551, 1.7129579782485962, 1.765480875968933, 2.816258192062378, 2.24301815032959, 2.134612560272217, 1.6361794471740723, 2.9011566638946533, 2.104402780532837, 2.9594414234161377, 1.47380793094635, 2.1529221534729004, 1.4044331312179565, 1.8284454345703125, 2.164560556411743, 1.422987937927246, 1.5019559860229492, 2.377633810043335, 2.5837225914001465, 2.34572696685791, 2.0311975479125977, 1.910585880279541, 1.1127821207046509, 1.6030129194259644, 2.2956361770629883, 2.1896791458129883, 2.059157371520996, 2.359015464782715, 2.5035486221313477, 1.8654934167861938, 1.836396336555481, 2.9754016399383545, 2.0071184635162354, 0.8971332907676697, 1.8410329818725586, 2.263514280319214, 2.9765331745147705, 1.6705776453018188, 3.162644624710083, 2.5947093963623047, 2.8620529174804688, 1.8392647504806519, 2.1796255111694336, 2.3237788677215576, 2.0181591510772705, 1.5323052406311035, 2.4858925342559814, 1.4735268354415894, 2.5419626235961914, 1.5159918069839478, 1.3892769813537598, 2.191995859146118, 2.2041399478912354, 0.13861148059368134, 0.09478065371513367, 0.08098623156547546, 0.09933101385831833, 0.06853772699832916, 0.15734712779521942, 0.08258770406246185, 0.17736941576004028, 0.1126253604888916, 0.12826114892959595, 0.10184550285339355, 0.12925492227077484, 0.11712338030338287, 0.20233885943889618, 0.0862511619925499, 0.07041734457015991, 0.10739120841026306, 0.13364754617214203, 0.07277315855026245, 0.1310194581747055, 0.17215506732463837, 0.11893846094608307, 0.008174629881978035, 0.06506863236427307, 0.13792352378368378, 0.10117058455944061, 0.09886228293180466, 0.07799894362688065, 0.16057193279266357, 0.0922369733452797, 0.06696034967899323, 0.10041635483503342, 0.0932457447052002, 0.12348242849111557, 0.14205311238765717, 0.06934678554534912, 0.08592408150434494, 0.04411492869257927, 0.08183741569519043, 0.07233793288469315, 0.10080172121524811, 0.09265638887882233, 0.11091184616088867, 0.025167707353830338, 0.12590011954307556, 0.06453382968902588, 0.03515511751174927, 0.08861137926578522, 0.08390843868255615, 0.08664464950561523, 0.16269710659980774, 0.06819156557321548, 0.12253076583147049, 0.1638832986354828, 0.10348052531480789, 0.10341113805770874, 0.09516959637403488, 0.015251359902322292, 0.0676620602607727, 0.11964324861764908, 0.0831218957901001, 0.08229504525661469, 0.11026189476251602, 0.1587291806936264, 0.12159734219312668, 0.08808636665344238, 0.0893595889210701, 0.0922098159790039, 0.11324339359998703, 0.055562227964401245, 0.12582091987133026, 0.10777174681425095, 0.0921609029173851, 0.060989320278167725, 0.121185302734375, 0.15505677461624146, 0.056223466992378235, 0.09300664812326431, 0.024288935586810112, 0.09923221170902252, 0.05586318299174309, 0.07533061504364014, 0.0891931802034378, 0.06719829142093658, 0.17643344402313232, 0.10306376218795776, 0.07472018152475357, 0.08043460547924042, 0.04049411043524742, 0.07170546054840088, 0.12477120757102966, 0.017430126667022705, 0.1525048166513443, 0.06410719454288483, 0.06202176585793495, 0.19750934839248657, 0.07348136603832245, 0.07912285625934601, 0.07623892277479172, 0.06327895075082779, 0.06685418635606766, 0.09037157148122787, 0.10259705036878586, 0.09828490763902664, 0.09771163761615753, 0.060789696872234344, 0.0921829417347908, 0.09067811816930771, 0.13297171890735626, 0.08642254024744034, 0.03537559509277344, 0.1151055321097374, 0.111269012093544, 0.09205882996320724, 0.11462213099002838, 0.10803254693746567, 0.02118319272994995, 0.12578889727592468, 0.1471003293991089, 0.06201392039656639, 0.10627111047506332, 0.13873307406902313, 0.04099653661251068, 0.08975673466920853, 0.027510037645697594, 0.12033586204051971, 0.1400003731250763, 0.06307633966207504, 0.16814063489437103, 0.11478545516729355, 0.11957038938999176, 0.15709388256072998, 0.06411375850439072, 0.1317845731973648, 0.09069538861513138, 0.09790752083063126, 0.04059784859418869, 0.1274237483739853, 0.07709091156721115, 0.11878781765699387, 0.1033506914973259, 0.162220761179924, 0.10523348301649094, 0.1672525703907013, 0.06013373285531998, 0.10468555986881256, 0.07120227068662643, 0.03818119317293167, 0.04191959276795387, 0.10590911656618118, 0.08030736446380615, 0.13521885871887207, 0.07999350130558014, 0.10665639489889145, 0.05571715533733368, 0.062283072620630264, 0.09840971976518631, 0.16266584396362305, 0.10503660142421722, 0.13553422689437866, 0.10047008097171783, 0.06096282973885536, 0.08227699995040894, 0.10285554826259613, 0.028236929327249527, 0.11626254767179489, 0.18855376541614532, 0.05828583240509033, 0.1338724046945572, 0.13533733785152435, 0.14410239458084106, 0.042159684002399445, 0.05308874323964119, 0.10639563947916031, 0.07564224302768707, 0.013708001933991909, 0.13813674449920654, 0.1008257269859314, 0.08165277540683746, 0.1036713644862175, 0.09693500399589539, 0.0859484076499939, 0.1147870421409607, 0.07225167751312256, 0.11838102340698242, 0.10404828190803528, 0.13281570374965668, 0.11054328829050064, 0.0547068789601326, 0.11895173788070679, 0.029401296749711037, 0.10353823751211166, 0.15027782320976257, 0.10741480439901352, 0.14824853837490082, 0.05683721974492073, 0.17930904030799866, 0.021618545055389404, 0.05433142930269241, 0.12719488143920898, 0.06762732565402985, 0.0752900242805481, 0.06861616671085358, 0.15471309423446655, 0.09737285226583481, 0.08357522636651993, 0.20843465626239777, 0.16179519891738892, 0.11024206876754761, 0.07403052598237991, 0.03741776943206787, 0.1621243953704834, 0.07692214101552963, 0.16308806836605072, 0.22054100036621094, 0.045963943004608154, 0.07817667722702026, 0.06880443543195724, 0.07468133419752121, 0.1336609274148941, 0.03992771357297897, 0.0924275666475296, 0.09914582967758179, 0.07344385981559753, 0.06318139284849167, 0.058983299881219864, 0.13308653235435486, 0.049989163875579834, 0.1415008008480072, 0.05616901442408562, 0.11428409069776535, 0.10748374462127686, 0.15380233526229858, 0.1127403974533081, 0.08278334140777588, 0.07484855502843857, 0.094329833984375, 0.08139511197805405, 0.060221798717975616, 0.0632413774728775, 0.06606150418519974, 0.14504799246788025, 0.07153720408678055, 0.12651284039020538, 0.11010627448558807, 0.09842132031917572, 0.08499562740325928, 0.08358881622552872, 0.051846206188201904, 0.1068125069141388, 0.12124327570199966, 0.031090740114450455, 0.08073723316192627, 0.1289827823638916, 0.1131824254989624, 0.03524461016058922, 0.16844415664672852, 0.13160887360572815, 0.08985575288534164, 0.13122773170471191, 0.13701455295085907, 0.08758044242858887, 0.11269574612379074, 0.07236878573894501, 0.10473262518644333, 0.09463675320148468, 0.08535724133253098, 0.09097171574831009, 0.1290074735879898, 0.1503109633922577, 0.09406393021345139, 0.10050822794437408, 0.1176229938864708, 0.056702494621276855, 0.07678718864917755, 0.11610917001962662, 0.08708108961582184, 0.07224307209253311, 0.09639811515808105, 0.0728604719042778, 0.037098467350006104, 0.15028853714466095, 0.1086340844631195, 0.17728030681610107, 0.09866868704557419, 0.0663151666522026, 0.17018531262874603, 0.08011768013238907, 0.12448513507843018, 0.08348968625068665, 0.10401828587055206, 0.050834111869335175, 0.049894049763679504, 0.06587134301662445, 0.1348026841878891, 0.08287042379379272, 0.1049007773399353, 0.08821225166320801, 0.11071550846099854, 0.046397626399993896, 0.8328275680541992, 0.6629704236984253, 0.9954774379730225, 0.7660833597183228, 0.42990827560424805, 0.41848814487457275, 0.25062933564186096, 0.452106773853302, 0.9006997346878052, 0.7682583928108215, 0.36890265345573425, 0.8017699718475342, 0.6533969044685364, 0.6461947560310364, 0.7808513641357422, 0.7938265800476074, 1.063041090965271, 0.6276237964630127, 0.428230881690979, 0.674139678478241, 0.35455459356307983, 0.635055422782898, 0.39818498492240906, 0.40140795707702637, 0.8731827139854431, 0.42486879229545593, 0.3054750859737396, 0.5851168632507324, 1.2606048583984375, 0.5754714012145996, 0.8513497710227966, 0.7762851715087891, 0.7093067169189453, 0.7293917536735535, 0.33986979722976685, 0.834824800491333, 0.7766056060791016, 0.9906689524650574, 0.5706103444099426, 0.231663316488266, 0.7354058623313904, 1.3385097980499268, 0.5869249701499939, 0.9834562540054321, 0.9656802415847778, 1.134982943534851, 0.585046112537384, 0.1672029048204422, 0.3930586874485016, 0.5846784710884094, 0.7545436024665833, 0.7926543354988098, 0.6286934614181519, 0.8435885310173035, 0.5196890830993652, 1.0765748023986816, 0.7212862968444824, 0.663220226764679, 0.49752506613731384, 0.8235548138618469, 0.685922384262085, 0.30180710554122925, 0.5773647427558899, 0.2515103220939636, 0.6243313550949097, 1.1170881986618042, 0.6880456209182739, 0.7060763239860535, 0.20919854938983917, 1.1953389644622803, 1.063980221748352, 0.5994112491607666, 0.4909067749977112, 0.6354149580001831, 1.364207148551941, 0.46644020080566406, 0.7803288698196411, 0.45723438262939453, 0.7031571269035339, 0.505744993686676, 0.47358566522598267, 0.5386610627174377, 1.0708922147750854, 0.6297786235809326, 0.507805585861206, 0.7278249859809875, 0.7061253786087036, 0.6432918906211853, 0.30744826793670654, 0.8091633319854736, 0.2790476381778717, 0.4633493423461914, 0.8763123750686646, 0.8123008608818054, 0.5724503993988037, 0.8420596122741699, 0.7089875340461731, 0.5558952689170837, 0.8668384552001953, 0.5916236042976379, 0.8450257182121277, 0.7995516657829285, 0.33897820115089417, 0.5487223863601685, 0.7222480773925781, 0.7926562428474426, 0.4436575174331665, 0.30470937490463257, 0.8070837259292603, 0.7079054117202759, 0.9278175234794617, 1.2458893060684204, 0.5856642127037048, 0.46680259704589844, 0.1738211065530777, 0.7823086977005005, 0.3995453417301178, 0.7244364619255066, 1.1124323606491089, 0.3332560658454895, 1.034050464630127, 0.7118334174156189, 0.7732481360435486, 0.8643749952316284, 0.5727657079696655, 0.42629989981651306, 0.9567610025405884, 0.5971124768257141, 0.38964352011680603, 0.8139246106147766, 0.5119865536689758, 0.7457543611526489, 0.7539761662483215, 0.46775171160697937, 0.7272441983222961, 0.7414942979812622, 0.8590917587280273, 0.2807818055152893, 0.4949846863746643, 0.7113981246948242, 0.53931725025177, 0.4915041923522949, 0.47346025705337524, 1.0961582660675049, 0.403085857629776, 0.2834862470626831, 0.5398064255714417, 0.8213387727737427, 0.4506305158138275, 1.0812571048736572, 0.6283199787139893, 0.6941391825675964, 0.9649821519851685, 0.5792258977890015, 0.5876806974411011, 0.7161734700202942, 0.5576087236404419, 0.46220117807388306, 0.3043241798877716, 0.27694690227508545, 0.5714687705039978, 0.7190868258476257, 0.41625556349754333, 0.34874358773231506, 0.6123069524765015, 0.6303765177726746, 0.3113752007484436, 0.5509143471717834, 0.19265177845954895, 0.43959563970565796, 0.5644575953483582, 0.3449762761592865, 0.47053828835487366, 0.7202808856964111, 0.7904679179191589, 0.4578855037689209, 0.6550998687744141, 0.42907285690307617, 0.34096091985702515, 0.8882495164871216, 0.26598185300827026, 1.0896179676055908, 0.7102279663085938, 0.9028005599975586, 0.5712404847145081, 0.3148439824581146, 0.6077176332473755, 0.7515641450881958, 0.5947259664535522, 0.47352686524391174, 1.0391616821289062, 0.37988778948783875, 0.5535444021224976, 0.2579772472381592, 0.8668014407157898, 0.9120500087738037, 0.5672552585601807, 0.2072678953409195, 1.0478880405426025, 0.5674012303352356, 0.6193342804908752, 0.7664998173713684, 0.9066848754882812, 0.6515620350837708, 0.6384409666061401, 0.44111311435699463, 0.44476285576820374, 0.4156888425350189, 0.749535858631134, 0.9537472128868103, 0.7210993766784668, 0.5362139940261841, 0.6013475060462952, 0.5714417695999146, 0.6673871278762817, 0.7325388193130493, 0.8679821491241455, 0.47977790236473083, 0.6435357332229614, 0.4689410924911499, 0.384451299905777, 0.5543191432952881, 0.8173210024833679, 0.4516908824443817, 0.7002315521240234, 0.6362187266349792, 0.3776281774044037, 0.5272918343544006, 0.7278954386711121, 0.41293787956237793, 0.9179545640945435, 0.593896746635437, 0.16033343970775604, 0.49317625164985657, 0.25686705112457275, 0.3421905040740967, 0.5373440980911255, 0.6763573884963989, 0.6931518912315369, 0.3080897927284241, 0.6978982090950012, 0.3291304409503937, 0.2887814939022064, 0.8058999180793762, 0.5263799428939819, 0.6076590418815613, 0.35973110795021057, 0.3397603929042816, 0.511439323425293, 0.7102068066596985, 0.4528983235359192, 0.7120103240013123, 0.38593313097953796, 0.5823907256126404, 0.30697107315063477, 0.5285722017288208, 0.583518385887146, 0.6789610981941223, 0.5033559203147888, 0.4430103302001953, 0.2541615068912506, 0.9167525768280029, 0.4043391942977905, 0.6023855209350586, 0.6821635365486145, 0.7438643574714661, 0.5487922430038452, 0.4995171129703522, 0.5081839561462402, 0.5740601420402527, 0.45993316173553467, 0.4099971055984497, 0.28102758526802063, 0.3546867370605469, 0.6294230222702026, 0.45213037729263306, 1.2678800821304321, 0.45170095562934875, 0.6996378898620605, 1.176520824432373, 1.134230613708496, 0.5627174973487854, 0.6954866647720337, 0.8468062877655029, 0.3923424780368805, 0.28411754965782166, 0.4774293303489685, 0.8085976839065552, 0.5865887403488159, 0.6336137056350708, 0.4131184220314026, 0.5082709193229675, 1.0426502227783203, 0.4044996500015259, 0.8061012625694275, 0.27698206901550293, 0.5954130291938782, 0.20399709045886993, 0.40635359287261963, 1.3531687259674072, 53.338748931884766, 122.10579681396484, 27.514007568359375, 16.59516716003418, 88.6741714477539, 10.04188346862793, 31.27459716796875, 28.692411422729492, 47.80837631225586, 38.08880615234375, 18.485671997070312, 90.35659790039062, 49.159080505371094, 22.114730834960938, 75.78862762451172, 89.40966796875, 25.93287467956543, 65.55502319335938, 88.8089599609375, 51.54847717285156, 38.5910530090332, 14.971113204956055, 20.846210479736328, 24.94866943359375, 16.04039192199707, 45.6343994140625, 36.631317138671875, 60.193359375, 16.047088623046875, 113.98027801513672, 24.98603630065918, 144.00347900390625, 42.95135498046875, 44.8258056640625, 42.3603401184082, 36.31660461425781, 15.492401123046875, 66.71578979492188, 47.77768325805664, 70.28974151611328, 79.29547882080078, 15.992841720581055, 74.341064453125, 33.26396179199219, 23.253297805786133, 32.28678894042969, 62.83561325073242, 62.60190963745117, 47.57009506225586, 60.742156982421875, 13.13433837890625, 78.98059844970703, 55.31552505493164, 18.473312377929688, 47.125160217285156, 26.516891479492188, 30.501388549804688, 28.282766342163086, 47.19279861450195, 23.791488647460938, 63.42397689819336, 49.00042724609375, 12.449615478515625, 17.180328369140625, 49.42816162109375, 31.003585815429688, 15.859041213989258, 61.080291748046875, 16.69874382019043, 49.59541702270508, 30.627580642700195, 103.66094207763672, 81.37715911865234, 33.84027862548828, 81.4757308959961, 85.06169891357422, 47.24598693847656, 91.3421401977539, 38.54693603515625, 52.009521484375, 74.86210632324219, 107.79061889648438, 31.13916015625, 15.328643798828125, 39.0849609375, 31.86895751953125, 21.818832397460938, 125.01041412353516, 58.327693939208984, 115.9681396484375, 12.092437744140625, 17.685653686523438, 13.031478881835938, 26.807281494140625, 65.30307006835938, 68.1456069946289, 70.55763244628906, 19.94624137878418, 92.87090301513672, 19.65669059753418, 16.2908935546875, 12.015533447265625, 13.998676300048828, 19.491119384765625, 25.039154052734375, 115.41226196289062, 55.848445892333984, 90.92671966552734, 53.61304473876953, 15.712465286254883, 32.44044494628906, 14.553133010864258, 53.94894790649414, 39.63798522949219, 105.71099090576172, 36.96435546875, 56.99282455444336, 44.3154296875, 19.958770751953125, 50.07777404785156, 36.7412109375, 35.20501708984375, 22.8963565826416, 44.528656005859375, 42.59410095214844, 44.7640266418457, 181.2665557861328, 196.32415771484375, 68.36654663085938, 125.88679504394531, 69.85861206054688, 24.17629623413086, 40.48598861694336, 49.18986129760742, 30.428619384765625, 58.9207763671875, 20.9591064453125, 20.412078857421875, 12.127272605895996, 35.40008544921875, 59.47270202636719, 24.517562866210938, 15.330130577087402, 53.31936264038086, 36.80352783203125, 19.992782592773438, 23.745101928710938, 21.616580963134766, 16.02301025390625, 42.28428649902344, 38.59716796875, 14.703563690185547, 20.425521850585938, 84.31605529785156, 54.444183349609375, 44.09271240234375, 44.509315490722656, 19.115020751953125, 27.392152786254883, 20.3289794921875, 25.07474136352539, 33.51463317871094, 34.8636474609375, 102.68435668945312, 56.88713836669922, 58.63272476196289, 78.1884765625, 29.752601623535156, 55.66408920288086, 34.113895416259766, 23.95136833190918, 27.23883056640625, 85.20526123046875, 60.0318603515625, 40.014892578125, 29.15021324157715, 25.79197883605957, 66.74465942382812, 34.90638732910156, 47.662109375, 60.92153549194336, 47.30764389038086, 106.2111587524414, 83.82453155517578, 20.5347900390625, 64.45767211914062, 51.8946533203125, 105.52694702148438, 13.733062744140625, 93.57927703857422, 32.4007568359375, 54.099945068359375, 99.80448150634766, 38.686771392822266, 31.352567672729492, 16.375457763671875, 16.3055419921875, 70.79241943359375, 28.44229507446289, 36.06001281738281, 45.96814727783203, 26.879701614379883, 30.83860206604004, 23.92698097229004, 68.68852996826172, 53.11083984375, 23.784713745117188, 30.644882202148438, 54.83722686767578, 11.956007957458496, 47.600799560546875, 39.34999084472656, 15.006113052368164, 50.57619857788086, 41.51267623901367, 36.41213607788086, 44.06852340698242, 77.09379577636719, 72.986328125, 16.75732421875, 18.251449584960938, 140.9807891845703, 27.93505859375, 59.13999557495117, 80.83490753173828, 74.14900970458984, 29.473173141479492, 17.52859115600586, 28.399343490600586, 76.36531066894531, 73.75848388671875, 28.894277572631836, 58.66557312011719, 15.056406021118164, 34.26631164550781, 137.09356689453125, 36.230262756347656, 60.15262985229492, 23.99755859375, 31.434661865234375, 30.3753662109375, 19.188232421875, 93.53813934326172, 26.118452072143555, 56.177547454833984, 59.03213119506836, 37.77455520629883, 40.783935546875, 11.50799560546875, 36.402557373046875, 36.69801330566406, 27.9031982421875, 59.38481140136719, 34.92751693725586, 27.705739974975586, 63.09003829956055, 51.603363037109375, 44.22344970703125, 71.99380493164062, 11.32861328125, 52.63516616821289, 70.691650390625, 57.61122131347656, 30.104267120361328, 63.42815399169922, 53.18791198730469, 46.291526794433594, 15.387420654296875, 18.67667579650879, 57.56578063964844, 71.84634399414062, 47.70818328857422, 78.03011322021484, 24.494491577148438, 36.17094421386719, 44.571258544921875, 48.7692756652832, 36.736114501953125, 32.89356994628906, 28.37664794921875, 86.93959045410156, 43.23662185668945, 24.660478591918945, 75.37611389160156, 91.63321685791016, 34.96344757080078, 26.70762062072754, 17.6229248046875, 43.35505676269531, 40.51383972167969, 81.67902374267578, 13.723236083984375, 25.62948226928711, 40.17762756347656, 49.555423736572266, 15.210000038146973, 30.391263961791992, 53.04524230957031, 39.542694091796875, 132.06137084960938, 1.6241331100463867, 1.9946035146713257, 1.736506462097168, 1.9966223239898682, 2.4482946395874023, 2.2819879055023193, 1.3804863691329956, 2.8579940795898438, 2.0591609477996826, 1.9086949825286865, 2.486504554748535, 1.279915690422058, 2.221013069152832, 3.111180305480957, 2.5377702713012695, 1.9029053449630737, 2.7744743824005127, 1.8810333013534546, 1.4386281967163086, 1.9223772287368774, 2.4410698413848877, 2.0302770137786865, 1.4531192779541016, 1.9351806640625, 2.1041977405548096, 2.242504119873047, 1.5908567905426025, 2.773759126663208, 1.325394868850708, 2.120422601699829, 3.7912309169769287, 2.1798200607299805, 1.6637998819351196, 1.6743706464767456, 2.252335548400879, 2.8258697986602783, 2.7766125202178955, 2.1764862537384033, 2.5506374835968018, 2.42014217376709, 2.11197829246521, 2.0800790786743164, 1.4559545516967773, 2.20034122467041, 3.474379301071167, 1.8070287704467773, 2.222468614578247, 2.4307310581207275, 2.237291097640991, 1.9907768964767456, 1.9945244789123535, 1.7889682054519653, 2.256213665008545, 3.024792432785034, 2.435683250427246, 2.838263988494873, 2.3258962631225586, 1.4525612592697144, 0.7870413661003113, 2.294733762741089, 2.206618309020996, 2.9319658279418945, 1.9732128381729126, 3.5117387771606445, 1.6748275756835938, 1.9911043643951416, 2.8372280597686768, 1.9800901412963867, 1.4142489433288574, 1.838733196258545, 2.085697650909424, 2.5799286365509033, 1.9695806503295898, 1.2645081281661987, 3.0870654582977295, 2.392083168029785, 2.123072385787964, 1.936647891998291, 2.541285514831543, 2.58176326751709, 1.411110758781433, 2.8998756408691406, 1.9589171409606934, 2.482069969177246, 2.29659366607666, 1.804604411125183, 1.8752254247665405, 1.3622475862503052, 1.4496564865112305, 2.5743134021759033, 1.4515923261642456, 1.9634865522384644, 1.685765027999878, 3.3453898429870605, 1.7245616912841797, 1.2088898420333862, 2.1405389308929443, 1.631589651107788, 2.3104753494262695, 2.44907546043396, 1.4484364986419678, 2.0559020042419434, 2.2867488861083984, 3.0660274028778076, 2.078191041946411, 2.254380702972412, 2.2531917095184326, 2.6521379947662354, 1.9730048179626465, 2.0925705432891846, 1.1339635848999023, 1.658740758895874, 1.6251269578933716, 1.5679632425308228, 3.28692364692688, 2.161119222640991, 2.7967119216918945, 1.6350868940353394, 2.6106274127960205, 1.2477446794509888, 2.930825710296631, 2.269686698913574, 2.9721531867980957, 1.2377948760986328, 2.002152681350708, 2.249192714691162, 1.4039963483810425, 1.7510422468185425, 1.505121111869812, 2.4706430435180664, 1.7293272018432617, 1.3097896575927734, 2.0930800437927246, 3.2263782024383545, 2.399331569671631, 1.4518753290176392, 1.5965603590011597, 1.9358434677124023, 3.8298964500427246, 1.9676153659820557, 3.0451934337615967, 1.8295756578445435, 1.985636591911316, 1.4544838666915894, 1.1224839687347412, 1.354304313659668, 1.9677153825759888, 1.4949849843978882, 2.7459747791290283, 2.8986175060272217, 2.1496801376342773, 2.195624351501465, 2.3096084594726562, 1.2767304182052612, 2.606346368789673, 1.6112884283065796, 1.6461135149002075, 1.4712404012680054, 2.9810192584991455, 1.2913912534713745, 1.6022074222564697, 1.664262294769287, 1.5884548425674438, 2.539052963256836, 1.873706340789795, 2.57028865814209, 2.4224963188171387, 1.3111305236816406, 2.251584053039551, 2.3248589038848877, 2.8869194984436035, 1.3045415878295898, 2.1983566284179688, 2.313433885574341, 2.565988063812256, 3.2061853408813477, 1.6043577194213867, 2.060748338699341, 1.9451687335968018, 1.3870229721069336, 1.8354367017745972, 1.3820457458496094, 3.299393892288208, 2.0864217281341553, 1.5190601348876953, 3.476719856262207, 2.2577428817749023, 2.3458073139190674, 2.1482961177825928, 1.1843023300170898, 2.0316991806030273, 2.4323549270629883, 1.5955700874328613, 2.042403221130371, 1.2568062543869019, 1.8088788986206055, 2.3911635875701904, 1.9254074096679688, 1.2255654335021973, 2.861701011657715, 3.4309892654418945, 2.9371232986450195, 2.0063438415527344, 1.793477177619934, 1.6655815839767456, 1.8072212934494019, 2.544621467590332, 2.0000851154327393, 1.1382895708084106, 1.7517375946044922, 2.6997733116149902, 2.3598098754882812, 2.571455240249634, 2.3885247707366943, 1.946027159690857, 2.1036250591278076, 3.6827309131622314, 1.6970757246017456, 2.068819761276245, 2.494384288787842, 1.6321479082107544, 1.5449761152267456, 1.6313482522964478, 1.8599992990493774, 2.107193946838379, 1.9234719276428223, 1.8265944719314575, 1.364790916442871, 2.5263125896453857, 2.0594229698181152, 1.7362946271896362, 1.4413793087005615, 2.231438636779785, 1.1661616563796997, 3.0953948497772217, 2.459531545639038, 3.2047462463378906, 1.8587942123413086, 3.3613719940185547, 2.422764778137207, 1.4468239545822144, 2.68813419342041, 2.1734018325805664, 1.3874263763427734, 2.841292142868042, 2.6759252548217773, 2.820342540740967, 1.3033981323242188, 1.942707896232605, 1.3317131996154785, 1.9667352437973022, 1.6285390853881836, 1.7980632781982422, 2.8068764209747314, 1.8276180028915405, 2.867299795150757, 2.3259878158569336, 1.9504863023757935, 2.279171943664551, 1.3251371383666992, 2.085468292236328, 1.8469475507736206, 1.760337471961975, 1.9904159307479858, 1.5556963682174683, 2.231593132019043, 1.7264717817306519, 1.314414143562317, 1.8803271055221558, 1.8503377437591553, 2.008525848388672, 1.7823957204818726, 1.1159638166427612, 2.273951768875122, 1.7431658506393433, 2.753922700881958, 2.061312198638916, 2.4133124351501465, 3.046051025390625, 1.8607991933822632, 1.6753933429718018, 2.3873071670532227, 1.5245128870010376, 2.1149702072143555, 2.518144369125366, 2.486546516418457, 1.7531365156173706, 2.909409999847412, 1.7528945207595825, 2.6512651443481445, 1.989030122756958, 2.4042842388153076, 2.20794677734375, 2.088282585144043, 1.6891698837280273, 2.0458171367645264, 3.0633223056793213, 1.613649606704712, 1.3889645338058472, 1.8287419080734253, 0.08168129622936249, 0.124298095703125, 0.029911350458860397, 0.10282675176858902, 0.07191246002912521, 0.03983437269926071, 0.1389511674642563, 0.13760016858577728, 0.05710573121905327, 0.11082044243812561, 0.11610984802246094, 0.10003542900085449, 0.09974944591522217, 0.11545338481664658, 0.036458950489759445, 0.03413376584649086, 0.10233339667320251, 0.09346935153007507, 0.13508129119873047, 0.11625784635543823, 0.15796957910060883, 0.12133439630270004, 0.07750464975833893, 0.118387371301651, 0.06370633840560913, 0.0799555853009224, 0.08073487877845764, 0.10268568992614746, 0.10188056528568268, 0.1185588464140892, 0.09589063376188278, 0.07649588584899902, 0.14848458766937256, 0.13574230670928955, 0.06908567249774933, 0.06389755010604858, 0.09819600731134415, 0.05788752809166908, 0.12349609285593033, 0.06075378134846687, 0.0790863037109375, 0.12832152843475342, 0.03844066709280014, 0.10407149791717529, 0.16970205307006836, 0.12438082695007324, 0.13127487897872925, 0.13610243797302246, 0.09719112515449524, 0.13502973318099976, 0.09319492429494858, 0.05702674388885498, 0.06118040904402733, 0.08765342831611633, 0.07547193020582199, 0.07948525249958038, 0.04220558702945709, 0.12730464339256287, 0.10806870460510254, 0.06117749214172363, 0.13755473494529724, 0.08445586264133453, 0.07423030585050583, 0.10529851913452148, 0.13278016448020935, 0.06897314637899399, 0.02652585692703724, 0.1454218327999115, 0.14847789704799652, 0.11368837207555771, 0.14093494415283203, 0.16059990227222443, 0.05982191488146782, 0.07602342218160629, 0.1339430809020996, 0.06495589017868042, 0.06054465100169182, 0.15305137634277344, 0.10055426508188248, 0.1825242042541504, 0.18250985443592072, 0.11075933277606964, 0.023759404197335243, 0.1509014517068863, 0.11295684427022934, 0.06857411563396454, 0.024202290922403336, 0.09014936536550522, 0.0714644342660904, 0.11620893329381943, 0.07573306560516357, 0.1358891874551773, 0.0366751030087471, 0.1042943149805069, 0.06296547502279282, 0.06385266780853271, 0.1032036766409874, 0.030581159517169, 0.09285293519496918, 0.09067707508802414, 0.15441419184207916, 0.07402633130550385, 0.0871681198477745, 0.04266207665205002, 0.08032165467739105, 0.10922334343194962, 0.06971615552902222, 0.18359234929084778, 0.06732194125652313, 0.07133866101503372, 0.13180653750896454, 0.070254847407341, 0.17536555230617523, 0.1643037050962448, 0.11412972211837769, 0.09641292691230774, 0.05765964463353157, 0.06479205936193466, 0.11451864242553711, 0.07633679360151291, 0.12324433773756027, 0.1055193841457367, 0.1191427931189537, 0.11887799948453903, 0.06355876475572586, 0.12196656316518784, 0.07741636037826538, 0.05252361297607422, 0.07398976385593414, 0.09526116400957108, 0.1263275444507599, 0.00691742030903697, 0.0930057018995285, 0.05521035194396973, 0.08555266261100769, 0.1457943469285965, 0.09218984097242355, 0.0644344910979271, 0.12719380855560303, 0.05749202519655228, 0.12269817292690277, 0.06187974289059639, 0.11686824262142181, 0.1288139373064041, 0.14554853737354279, 0.08089800924062729, 0.02639607898890972, 0.03776801377534866, 0.1508716344833374, 0.16626985371112823, 0.0707283690571785, 0.08532687276601791, 0.09522687643766403, 0.08995656669139862, 0.15964050590991974, 0.06805186718702316, 0.09089189022779465, 0.09958601742982864, 0.1010211706161499, 0.15087278187274933, 0.13764743506908417, 0.08360134065151215, 0.07034105062484741, 0.1380530297756195, 0.08753311634063721, 0.08885104209184647, 0.10663653910160065, 0.06603667885065079, 0.12073802947998047, 0.06971967220306396, 0.1407489776611328, 0.07183165103197098, 0.08237777650356293, 0.05942706763744354, 0.11641097068786621, 0.0776219442486763, 0.12196773290634155, 0.046526823192834854, 0.1062500923871994, 0.16427679359912872, 0.10522901266813278, 0.12715572118759155, 0.06980933994054794, 0.07607854157686234, 0.08962587267160416, 0.14057427644729614, 0.09567863494157791, 0.11519330739974976, 0.1808197945356369, 0.08821287006139755, 0.05742105841636658, 0.07859586924314499, 0.08733045309782028, 0.07394707947969437, 0.15505504608154297, 0.17633983492851257, 0.12157659977674484, 0.06211631000041962, 0.15986765921115875, 0.10140328854322433, 0.10946493595838547, 0.11351633816957474, 0.11120258271694183, 0.10629840940237045, 0.1067766547203064, 0.15365241467952728, 0.134705051779747, 0.056273482739925385, 0.10142235457897186, 0.10606910288333893, 0.06768470257520676, 0.08756148815155029, 0.08882347494363785, 0.09619016200304031, 0.10787837952375412, 0.1357256919145584, 0.10021898150444031, 0.16133059561252594, 0.09319204837083817, 0.05138248950242996, 0.15959450602531433, 0.14856883883476257, 0.06975579261779785, 0.11159923672676086, 0.19231632351875305, 0.08779002726078033, 0.0788378193974495, 0.10182544589042664, 0.12459685653448105, 0.05831744521856308, 0.11331184208393097, 0.06603014469146729, 0.08990112692117691, 0.13858456909656525, 0.14648978412151337, 0.09915022552013397, 0.09322769939899445, 0.12083455920219421, 0.15012651681900024, 0.07921049743890762, 0.055451229214668274, 0.1092107817530632, 0.0447617806494236, 0.06840912252664566, 0.10962878912687302, 0.11627330631017685, 0.05224926024675369, 0.09258455038070679, 0.10485156625509262, 0.10494203120470047, 0.12743976712226868, 0.11705359816551208, 0.17421351373195648, 0.09063299000263214, 0.0901397243142128, 0.12433189153671265, 0.11239931732416153, 0.05181357264518738, 0.09186050295829773, 0.10732049494981766, 0.08227232843637466, 0.04416472837328911, 0.10437168180942535, 0.13738347589969635, 0.10479804873466492, 0.07882966846227646, 0.09816781431436539, 0.09139401465654373, 0.05082961916923523, 0.092470183968544, 0.155955508351326, 0.08667818456888199, 0.0772036463022232, 0.10844283550977707, 0.12231164425611496, 0.08050323277711868, 0.1576693058013916, 0.03849753364920616, 0.06384917348623276, 0.11280585825443268, 0.09452920407056808, 0.04069995880126953, 0.10342377424240112, 0.12039833515882492, 0.13555863499641418, 0.07762344926595688, 0.10086047649383545, 0.14747540652751923, 0.06813321262598038, 0.12916156649589539, 0.13664326071739197, 0.06898283213376999, 0.11146470159292221, 0.08698909729719162, 0.09959212690591812, 0.09192100167274475, 0.08363519608974457, 0.12223773449659348, 0.06756360828876495, 0.11611991375684738, 0.17476077377796173, 0.5756434202194214, 1.077362298965454, 0.7213579416275024, 1.3207861185073853, 0.5089338421821594, 1.1942906379699707, 0.3919321596622467, 1.0100016593933105, 0.47017234563827515, 0.5591511130332947, 0.6712306141853333, 0.8359795808792114, 0.7298862934112549, 0.7524354457855225, 0.5849846601486206, 0.6753530502319336, 0.09230063110589981, 0.38507381081581116, 0.8848469257354736, 0.5660338401794434, 0.7485421299934387, 0.7832108736038208, 0.6134764552116394, 0.8345609903335571, 0.7106901407241821, 0.8634390830993652, 0.45128554105758667, 0.6639992594718933, 0.4620642066001892, 0.9337986707687378, 0.9533866047859192, 0.712139904499054, 0.7052438855171204, 0.47253352403640747, 0.3777964413166046, 0.6336773633956909, 0.8758509755134583, 0.843865692615509, 0.479000449180603, 1.0937014818191528, 0.5531582236289978, 0.9873461723327637, 0.766086995601654, 0.803292453289032, 0.23268310725688934, 0.9681223034858704, 0.5066463947296143, 0.46589088439941406, 0.898922860622406, 0.6749998331069946, 0.7879743576049805, 0.8631576895713806, 0.8032081127166748, 0.32199960947036743, 0.5084076523780823, 0.5301980376243591, 0.6251165866851807, 0.15835963189601898, 0.6148200035095215, 0.8514642119407654, 0.27274829149246216, 0.8499200940132141, 0.673965334892273, 0.5670071840286255, 0.7539281845092773, 0.4517941176891327, 0.8625991344451904, 1.1417391300201416, 0.4496196508407593, 0.7062854766845703, 0.5896427035331726, 0.6633898019790649, 0.9455716013908386, 0.8014869689941406, 0.24306975305080414, 0.6968989372253418, 0.6587883830070496, 0.5783853530883789, 0.5240569710731506, 0.4364562928676605, 1.0607552528381348, 0.8397446274757385, 0.8667312264442444, 0.6733788847923279, 0.9200706481933594, 0.6868864297866821, 0.7032722234725952, 0.5958618521690369, 0.8900134563446045, 0.4780302941799164, 1.1942435503005981, 0.5528733730316162, 0.7318469285964966, 0.3755826950073242, 0.6476348638534546, 1.0268752574920654, 0.9364097118377686, 0.523627758026123, 0.517437756061554, 0.7112367153167725, 0.8247158527374268, 1.0177146196365356, 0.6483745574951172, 1.3544479608535767, 0.40978866815567017, 0.8915621042251587, 0.77748042345047, 0.4508700370788574, 0.6077128648757935, 0.7651708722114563, 1.0092647075653076, 0.5891708731651306, 0.5043537616729736, 0.8002297282218933, 0.47200384736061096, 0.7707425355911255, 0.6143057942390442, 0.4572691321372986, 0.731357991695404, 0.7013476490974426, 0.9205134510993958, 0.31869176030158997, 0.6181964874267578, 0.3941665589809418, 0.43245917558670044, 0.7446575164794922, 0.3846670687198639, 0.27082526683807373, 1.1710882186889648, 0.562606155872345, 0.8617892265319824, 0.7295897603034973, 0.6868026852607727, 0.8359493613243103, 0.5311607718467712, 0.6089475750923157, 0.8784939646720886, 0.5613831877708435, 0.7605932354927063, 0.4480286240577698, 0.40797486901283264, 0.5082115530967712, 0.5609518885612488, 0.5062609314918518, 1.230272889137268, 0.4769344925880432, 0.4806228578090668, 0.6794245839118958, 0.8763414621353149, 0.7295408248901367, 0.9428650736808777, 0.48572149872779846, 0.791352391242981, 0.6257631778717041, 0.9762429594993591, 0.28954464197158813, 0.8316952586174011, 0.6653006672859192, 0.4403584897518158, 0.7209144234657288, 0.618690013885498, 0.9967600107192993, 0.5725688934326172, 0.6012469530105591, 0.34079787135124207, 0.8441479206085205, 1.1308469772338867, 0.9563526511192322, 1.035189151763916, 1.132565975189209, 0.3902722895145416, 0.9637743234634399, 0.6985394358634949, 0.7471685409545898, 0.4439624547958374, 0.2788131535053253, 0.31753796339035034, 1.1334152221679688, 0.8970255851745605, 1.0042043924331665, 0.5574296712875366, 0.2210855782032013, 0.9797461628913879, 0.4853335916996002, 0.6559354066848755, 0.8000199794769287, 1.1636700630187988, 0.7994745373725891, 0.4883669316768646, 0.7643880844116211, 0.7489479184150696, 1.1608537435531616, 0.5661662220954895, 0.5889378786087036, 0.3828642964363098, 0.7438861131668091, 0.5787003040313721, 0.6004642844200134, 1.121888279914856, 0.5856099724769592, 0.7864561080932617, 0.8947966694831848, 0.439807653427124, 0.5031416416168213, 0.15311717987060547, 0.5461338758468628, 0.7765550017356873, 0.43834567070007324, 1.064950704574585, 0.41863006353378296, 0.8210029602050781, 1.031626582145691, 0.7475387454032898, 0.5408143401145935, 0.31044256687164307, 0.6283228397369385, 0.9107401967048645, 0.4409106969833374, 0.4420149028301239, 0.39534705877304077, 0.6425188183784485, 0.43764448165893555, 0.7485855221748352, 0.8297083973884583, 0.3352636396884918, 0.4623359441757202, 1.033581018447876, 0.7102738618850708, 0.3312687873840332, 0.5961437225341797, 0.6178786754608154, 0.6118373870849609, 0.41556745767593384, 0.3164424002170563, 0.8015727996826172, 0.7485531568527222, 1.0491039752960205, 0.7945278882980347, 0.5489747524261475, 0.9608920216560364, 0.5746616721153259, 1.0693984031677246, 0.9143242239952087, 0.4623940587043762, 0.6149170398712158, 1.083662748336792, 1.0495400428771973, 0.48226743936538696, 0.9580119252204895, 0.419912189245224, 0.5049793720245361, 0.3307653069496155, 0.2837357521057129, 0.4982558786869049, 0.6209173202514648, 1.1205755472183228, 0.4870661795139313, 0.7126820087432861, 0.455678790807724, 0.3841618597507477, 0.3019063174724579, 0.3572472631931305, 0.5969988703727722, 0.5195136666297913, 0.15864317119121552, 0.4103965759277344, 0.7821162343025208, 0.8089867830276489, 0.42147862911224365, 0.8301423192024231, 0.7373602986335754, 0.5996259450912476, 0.556288480758667, 0.7557604908943176, 1.0274478197097778, 0.6069931387901306, 0.6168491840362549, 0.5351033806800842, 0.5239317417144775, 0.8429964184761047, 0.772445797920227, 0.44320523738861084, 0.6119047403335571, 0.4972408711910248, 0.5692005753517151, 0.5303615927696228, 0.2850348949432373, 0.4334319829940796, 0.663560152053833, 0.5485942363739014, 1.378822922706604, 0.6886416673660278, 0.546913206577301, 0.6500747799873352, 0.3533852994441986, 0.41929319500923157, 1.216837763786316, 0.5466165542602539, 0.7330383062362671, 55.91420364379883, 29.663330078125, 38.45806121826172, 49.22865295410156, 136.80152893066406, 41.87124252319336, 84.91175842285156, 82.29634857177734, 16.16550064086914, 35.97256088256836, 65.19961547851562, 20.89752197265625, 50.39854431152344, 55.36907958984375, 20.871854782104492, 59.84588623046875, 35.323333740234375, 71.3016357421875, 51.94961166381836, 71.67176818847656, 17.24323844909668, 13.174077033996582, 92.40943908691406, 22.21558952331543, 16.283052444458008, 49.846923828125, 68.79594421386719, 115.92286682128906, 68.52384185791016, 79.97323608398438, 21.219482421875, 28.529447555541992, 61.01433563232422, 37.3592529296875, 23.793119430541992, 52.58329391479492, 82.58968353271484, 56.147727966308594, 26.532333374023438, 58.249114990234375, 14.428515434265137, 19.404754638671875, 169.6630096435547, 117.56471252441406, 53.243953704833984, 17.06658935546875, 27.005277633666992, 155.35342407226562, 12.026591300964355, 102.75112915039062, 15.07574462890625, 71.11834716796875, 42.307273864746094, 40.827972412109375, 62.24628829956055, 15.130722045898438, 16.9123477935791, 53.40544128417969, 52.30846405029297, 16.43882179260254, 131.1591339111328, 60.98683547973633, 63.215457916259766, 17.0313720703125, 61.321136474609375, 91.8213882446289, 65.92230224609375, 38.6829833984375, 53.931365966796875, 84.40557098388672, 17.889129638671875, 50.17958450317383, 80.89612579345703, 27.650644302368164, 13.818398475646973, 15.246856689453125, 49.76074981689453, 51.84987258911133, 57.40114974975586, 16.50830078125, 48.27399826049805, 57.918270111083984, 22.575136184692383, 45.06472396850586, 24.25958251953125, 42.68272018432617, 140.11366271972656, 39.58304977416992, 61.183685302734375, 88.5897216796875, 35.93571472167969, 46.06441116333008, 81.5421142578125, 13.048828125, 93.2393569946289, 103.0920181274414, 24.21107292175293, 35.83046340942383, 71.72164154052734, 67.33251953125, 24.1358642578125, 47.6005859375, 92.9388656616211, 21.652992248535156, 12.10235595703125, 50.346473693847656, 17.646820068359375, 20.04827880859375, 67.91791534423828, 15.70794677734375, 47.25087356567383, 20.625579833984375, 12.711645126342773, 14.2138671875, 19.161514282226562, 101.41997528076172, 142.4965057373047, 22.619354248046875, 17.15032958984375, 39.9659423828125, 66.47515869140625, 22.718862533569336, 24.45404815673828, 61.477020263671875, 33.47109603881836, 60.44318389892578, 26.87607192993164, 112.01416015625, 10.743727684020996, 45.80913162231445, 33.619903564453125, 54.812801361083984, 42.50236129760742, 20.522611618041992, 73.50883483886719, 50.62757110595703, 80.90364074707031, 55.759368896484375, 20.402442932128906, 19.773971557617188, 37.61924743652344, 33.55788803100586, 18.167448043823242, 13.007110595703125, 62.25751876831055, 102.2616958618164, 21.13612174987793, 93.39132690429688, 141.0673828125, 50.29315185546875, 60.80390548706055, 205.53271484375, 29.510438919067383, 14.010051727294922, 16.227603912353516, 14.258224487304688, 21.630287170410156, 20.958646774291992, 12.165679931640625, 45.6732177734375, 54.32770538330078, 52.206634521484375, 66.09521484375, 51.46803665161133, 53.45212936401367, 65.63986206054688, 39.34063720703125, 46.26837921142578, 112.77163696289062, 31.78887176513672, 111.8080825805664, 27.99749755859375, 52.34346389770508, 61.0853271484375, 22.58511734008789, 143.0455780029297, 18.445207595825195, 52.27723693847656, 16.982328414916992, 34.15085220336914, 33.19654083251953, 16.880401611328125, 26.487489700317383, 65.95401000976562, 31.466197967529297, 33.76177978515625, 83.1177749633789, 18.047460556030273, 67.57553100585938, 92.46356201171875, 64.39606475830078, 35.62266540527344, 23.278636932373047, 81.3192138671875, 48.43377685546875, 20.782958984375, 50.44228744506836, 90.8202133178711, 27.80058479309082, 17.21026611328125, 35.60441589355469, 163.63299560546875, 17.96209716796875, 27.290966033935547, 18.54511833190918, 103.19780731201172, 53.45232391357422, 43.61279296875, 31.41180419921875, 42.70212936401367, 30.619354248046875, 66.52104949951172, 12.218673706054688, 15.070785522460938, 15.79278564453125, 26.983327865600586, 159.61392211914062, 39.9649658203125, 32.66797637939453, 21.656156539916992, 16.239105224609375, 84.5595703125, 99.33946990966797, 16.1182861328125, 45.85890579223633, 51.29616928100586, 51.92612838745117, 42.739593505859375, 111.56243896484375, 78.5877685546875, 77.138916015625, 13.534027099609375, 15.64898681640625, 111.44786834716797, 40.0074462890625, 23.336471557617188, 57.8994140625, 49.03529739379883, 37.454681396484375, 106.78571319580078, 50.495452880859375, 49.67333984375, 46.330169677734375, 62.09075927734375, 17.6453857421875, 51.951751708984375, 65.97098541259766, 36.499332427978516, 62.076171875, 11.994403839111328, 18.99244499206543, 25.682708740234375, 32.95654296875, 86.73800659179688, 31.87027359008789, 115.41109466552734, 49.67871856689453, 98.0208969116211, 17.46918296813965, 50.4005012512207, 67.56710815429688, 130.0784912109375, 67.4166030883789, 81.10820770263672, 19.148834228515625, 25.459413528442383, 37.54861068725586, 24.263916015625, 13.532760620117188, 41.096492767333984, 52.07649612426758, 51.0102424621582, 56.902099609375, 14.93487548828125, 28.257633209228516, 35.11138916015625, 25.465951919555664, 52.35383605957031, 72.64401245117188, 44.600677490234375, 39.93179702758789, 26.0123291015625, 9.294052124023438, 15.165313720703125, 60.906551361083984, 35.12277603149414, 19.51202392578125, 48.610897064208984, 24.96356201171875, 17.316436767578125, 18.237899780273438, 53.433837890625, 16.37586784362793, 90.8475341796875, 49.57902145385742, 66.77044677734375, 50.57468795776367, 17.014755249023438, 29.6243896484375, 27.5430908203125, 2.5006251335144043, 1.927840232849121, 1.6165741682052612, 2.4939377307891846, 3.200110912322998, 1.754783034324646, 1.59187650680542, 2.3615334033966064, 2.677150011062622, 2.453132152557373, 2.155877113342285, 2.4311091899871826, 1.5715017318725586, 1.3401919603347778, 1.6626622676849365, 1.5944271087646484, 1.6921411752700806, 1.7171735763549805, 1.0869024991989136, 1.1545367240905762, 1.6018798351287842, 2.7014129161834717, 1.363230586051941, 2.1482770442962646, 2.1685874462127686, 2.285828113555908, 1.4898041486740112, 2.2416951656341553, 2.469357490539551, 2.354288101196289, 2.466792106628418, 1.5740842819213867, 1.4513304233551025, 1.6880910396575928, 1.6096487045288086, 1.4396849870681763, 2.405388832092285, 2.15579891204834, 2.6777923107147217, 1.5749672651290894, 2.7242534160614014, 1.5866804122924805, 1.9545975923538208, 2.893019437789917, 2.3190596103668213, 2.1489861011505127, 1.789143681526184, 1.9088540077209473, 2.1666901111602783, 2.98948073387146, 2.4933671951293945, 2.2384448051452637, 2.175990104675293, 1.6952719688415527, 2.0488827228546143, 2.5720226764678955, 2.071347236633301, 1.3689278364181519, 1.3303985595703125, 2.0510072708129883, 3.2661101818084717, 2.9323832988739014, 1.991719365119934, 1.4905996322631836, 2.321845054626465, 2.5653393268585205, 2.530834674835205, 1.407244324684143, 2.848846435546875, 2.567324161529541, 2.2804784774780273, 1.6423553228378296, 1.7837799787521362, 2.568218946456909, 1.9716243743896484, 2.5104167461395264, 2.6027934551239014, 2.7430145740509033, 2.3128719329833984, 2.4585695266723633, 3.211796760559082, 2.511113405227661, 1.8543524742126465, 2.58022403717041, 2.7405426502227783, 1.880385398864746, 1.543160319328308, 1.9121216535568237, 2.9121901988983154, 1.3675909042358398, 1.4970921277999878, 3.7795655727386475, 1.974898338317871, 1.8697556257247925, 1.8090828657150269, 1.395182728767395, 1.2174636125564575, 1.5957201719284058, 2.471799612045288, 2.3257265090942383, 2.5864837169647217, 2.2756357192993164, 1.7508602142333984, 1.981148600578308, 1.9475029706954956, 3.255246877670288, 2.573556423187256, 2.524228811264038, 1.943467617034912, 2.12551212310791, 1.9746133089065552, 2.665424108505249, 1.4945560693740845, 1.3212664127349854, 2.4464900493621826, 1.584223747253418, 1.6380356550216675, 1.4723747968673706, 2.4388201236724854, 2.3781790733337402, 2.6024065017700195, 2.2132954597473145, 3.183053493499756, 1.928481101989746, 2.3107712268829346, 1.547577977180481, 2.139838457107544, 1.3492249250411987, 1.6814603805541992, 2.3283228874206543, 2.1367104053497314, 2.6758792400360107, 1.8869293928146362, 2.6879403591156006, 1.5493508577346802, 3.1929445266723633, 2.953303813934326, 2.1600301265716553, 1.9638738632202148, 1.8847808837890625, 3.24062442779541, 2.369962692260742, 2.129887580871582, 2.4472899436950684, 3.0123536586761475, 3.474043846130371, 2.0522992610931396, 2.0369911193847656, 1.9551409482955933, 1.7991074323654175, 2.5475974082946777, 3.207911252975464, 1.5208252668380737, 2.850062847137451, 2.0399649143218994, 1.4435871839523315, 1.1033493280410767, 2.041309118270874, 1.3616812229156494, 2.503396511077881, 2.104386329650879, 2.4047343730926514, 2.1647634506225586, 2.572711706161499, 1.5223461389541626, 2.8416528701782227, 1.8574094772338867, 0.7844748497009277, 1.9869168996810913, 2.457186460494995, 2.4761717319488525, 3.135241746902466, 1.4863226413726807, 2.618917226791382, 2.6877360343933105, 1.999129295349121, 1.346832513809204, 2.429011583328247, 1.0854781866073608, 1.4046567678451538, 2.666041135787964, 1.7824316024780273, 3.5650219917297363, 1.941262125968933, 1.337214469909668, 2.1232481002807617, 2.3658201694488525, 1.4113510847091675, 1.5193716287612915, 2.513598680496216, 1.8449056148529053, 1.3558251857757568, 2.159499406814575, 1.7428902387619019, 2.824845552444458, 2.305274724960327, 1.944701075553894, 1.5421684980392456, 1.1521962881088257, 3.3238346576690674, 1.3373008966445923, 2.44143009185791, 2.608449935913086, 1.942221999168396, 2.5566344261169434, 2.1902835369110107, 2.4339118003845215, 3.493628740310669, 2.971146821975708, 3.219703197479248, 3.351557731628418, 1.5003265142440796, 1.2958282232284546, 2.9425384998321533, 2.0818872451782227, 2.0349817276000977, 2.5684990882873535, 2.34915828704834, 1.7163039445877075, 2.217484474182129, 2.644662380218506, 2.0723767280578613, 2.694244384765625, 2.649747848510742, 1.809992790222168, 2.0257656574249268, 2.0914831161499023, 2.079333543777466, 2.1718568801879883, 1.5497105121612549, 2.6682024002075195, 2.0945818424224854, 2.3423051834106445, 2.3189189434051514, 1.4521191120147705, 1.438751220703125, 2.1327028274536133, 2.2378439903259277, 1.689956784248352, 3.0187389850616455, 2.3023550510406494, 1.4111547470092773, 2.313753843307495, 2.814347267150879, 2.016261100769043, 2.641101121902466, 1.827479362487793, 2.2583062648773193, 1.7184171676635742, 2.7172813415527344, 2.1474037170410156, 2.0519959926605225, 2.3267953395843506, 3.231081247329712, 3.0827419757843018, 1.4187722206115723, 3.260138511657715, 2.9885857105255127, 2.615767478942871, 1.872131586074829, 1.2710952758789062, 1.8042337894439697, 1.6579842567443848, 2.032862424850464, 1.6082323789596558, 3.3462975025177, 1.6736425161361694, 2.804429292678833, 1.634599208831787, 2.353332281112671, 1.9097862243652344, 2.0915462970733643, 1.8892736434936523, 1.781241774559021, 1.91901433467865, 3.0840044021606445, 1.9184484481811523, 1.8992300033569336, 1.8707436323165894, 1.7420339584350586, 3.06622314453125, 2.1407716274261475, 1.182481050491333, 1.6432245969772339, 2.3011112213134766, 1.14924955368042, 2.39755916595459, 1.932076334953308, 2.408440113067627, 2.199002265930176, 1.4699201583862305, 2.51721453666687, 1.3068283796310425, 2.3367087841033936, 1.4922726154327393, 3.490790367126465, 2.3498311042785645, 2.530524492263794, 1.4061803817749023, 2.328733444213867, 0.06570636481046677, 0.08907768130302429, 0.07531819492578506, 0.11013198643922806, 0.08776644617319107, 0.17079181969165802, 0.06500396877527237, 0.047260429710149765, 0.08592105656862259, 0.13500022888183594, 0.10553161054849625, 0.06510568410158157, 0.021216223016381264, 0.16823211312294006, 0.12934118509292603, 0.060271501541137695, 0.0423617921769619, 0.13173572719097137, 0.15236617624759674, 0.07001841813325882, 0.09628893435001373, 0.13602811098098755, 0.15067537128925323, 0.1852007657289505, 0.0667445957660675, 0.07402782142162323, 0.11743085831403732, 0.17153488099575043, 0.15026754140853882, 0.09344042837619781, 0.08163736015558243, 0.212746724486351, 0.16207240521907806, 0.10134871304035187, 0.07056081295013428, 0.07439374923706055, 0.08604145050048828, 0.08376797288656235, 0.0960826501250267, 0.12048375606536865, 0.12656603753566742, 0.05178142338991165, 0.10519925504922867, 0.08494215458631516, 0.12563815712928772, 0.12116481363773346, 0.0652114674448967, 0.0480489619076252, 0.09692676365375519, 0.11784309148788452, 0.11486838757991791, 0.07595422118902206, 0.17266328632831573, 0.09013023227453232, 0.11630485951900482, 0.1616637259721756, 0.14368019998073578, 0.128825843334198, 0.05764162912964821, 0.14315076172351837, 0.1691596508026123, 0.11641384661197662, 0.08356308937072754, 0.08480823040008545, 0.129958838224411, 0.13465294241905212, 0.10960125923156738, 0.06626904010772705, 0.07426399737596512, 0.0346495620906353, 0.07572024315595627, 0.06018788367509842, 0.08437341451644897, 0.060894329100847244, 0.1556641012430191, 0.1283354014158249, 0.1326155662536621, 0.09301786124706268, 0.07921487838029861, 0.08907730877399445, 0.0579531192779541, 0.11140186339616776, 0.12106061726808548, 0.16565975546836853, 0.057776473462581635, 0.06302591413259506, 0.10612393170595169, 0.1244872659444809, 0.07186827808618546, 0.1824578046798706, 0.09684243053197861, 0.08132029324769974, 0.047260455787181854, 0.14378243684768677, 0.07532291114330292, 0.07533235102891922, 0.08523624390363693, 0.15461891889572144, 0.10287650674581528, 0.11495284736156464, 0.03679737076163292, 0.09634099900722504, 0.10906857252120972, 0.07525160908699036, 0.06832243502140045, 0.12369067966938019, 0.09604137390851974, 0.07061611860990524, 0.07949480414390564, 0.10516940802335739, 0.08869775384664536, 0.14159564673900604, 0.13038310408592224, 0.06962317228317261, 0.1365690529346466, 0.049339212477207184, 0.13598963618278503, 0.05459332466125488, 0.07178526371717453, 0.12340249866247177, 0.08583839237689972, 0.2061351090669632, 0.10519266128540039, 0.12266340106725693, 0.05601383000612259, 0.10051294416189194, 0.1425180435180664, 0.19673465192317963, 0.13406674563884735, 0.07301414012908936, 0.0860012099146843, 0.12223535031080246, 0.10747051239013672, 0.24169974029064178, 0.11550372838973999, 0.12313271313905716, 0.05560092255473137, 0.059862494468688965, 0.07031802088022232, 0.12623284757137299, 0.04093300551176071, 0.16753894090652466, 0.09759566932916641, 0.12734733521938324, 0.09768933057785034, 0.08377029001712799, 0.09650087356567383, 0.1460808664560318, 0.12155372649431229, 0.08220602571964264, 0.06525001674890518, 0.11173396557569504, 0.12232883274555206, 0.13753104209899902, 0.10575796663761139, 0.11390142887830734, 0.09195762127637863, 0.11300212889909744, 0.24038799107074738, 0.20672281086444855, 0.10111190378665924, 0.1903579831123352, 0.11580825597047806, 0.05787559971213341, 0.03749210387468338, 0.16504104435443878, 0.1189480572938919, 0.14361904561519623, 0.05230093002319336, 0.09688528627157211, 0.09533733129501343, 0.08983667194843292, 0.09468131512403488, 0.13021081686019897, 0.11300124228000641, 0.06471604853868484, 0.06646538525819778, 0.11307886242866516, 0.060920197516679764, 0.1273215264081955, 0.05523693934082985, 0.10612644255161285, 0.08651771396398544, 0.0682288408279419, 0.15725266933441162, 0.11509740352630615, 0.11829376220703125, 0.04791443794965744, 0.1889788657426834, 0.172061949968338, 0.11283474415540695, 0.08786898106336594, 0.05455723777413368, 0.08461899310350418, 0.04123379662632942, 0.1345434933900833, 0.07828515022993088, 0.1513092815876007, 0.1041872501373291, 0.09192633628845215, 0.06633085012435913, 0.10288771986961365, 0.08454674482345581, 0.12532472610473633, 0.1280876249074936, 0.039102450013160706, 0.14406192302703857, 0.06589961051940918, 0.23065108060836792, 0.07953006029129028, 0.07739126682281494, 0.07200425863265991, 0.0635547935962677, 0.11031442135572433, 0.14060039818286896, 0.15824609994888306, 0.07424145936965942, 0.08161317557096481, 0.11436396092176437, 0.08924845606088638, 0.11122533679008484, 0.16384802758693695, 0.11544211208820343, 0.12001335620880127, 0.14956235885620117, 0.12902817130088806, 0.11604791134595871, 0.13014349341392517, 0.04450688138604164, 0.1352733075618744, 0.12425462156534195, 0.047928597778081894, 0.09136872738599777, 0.12824943661689758, 0.07680199295282364, 0.07955189794301987, 0.06436195224523544, 0.06370103359222412, 0.17215247452259064, 0.12616302073001862, 0.04960399493575096, 0.07437196373939514, 0.13942624628543854, 0.03358074650168419, 0.09152457863092422, 0.10275693982839584, 0.09256035834550858, 0.08642260730266571, 0.03372504189610481, 0.038694027811288834, 0.06722792237997055, 0.15821883082389832, 0.09010864794254303, 0.04653656482696533, 0.1774168759584427, 0.12031515687704086, 0.06420891731977463, 0.08447562903165817, 0.10226457566022873, 0.16213786602020264, 0.0941510871052742, 0.10322313010692596, 0.09075117111206055, 0.03828310966491699, 0.12379586696624756, 0.08702384680509567, 0.056367602199316025, 0.05826449394226074, 0.09159354865550995, 0.08277226239442825, 0.1442602574825287, 0.13516387343406677, 0.10795823484659195, 0.06276392191648483, 0.05519452318549156, 0.0644504576921463, 0.1146656945347786, 0.12113888561725616, 0.09819494932889938, 0.0718095451593399, 0.17690642178058624, 0.10994577407836914, 0.11438091844320297, 0.15664233267307281, 0.08928824961185455, 0.05866897851228714, 0.0742160975933075, 0.07909750938415527, 0.12447387725114822, 0.13548892736434937, 0.11951299756765366, 0.04870801791548729, 0.10743894428014755, 0.08052455633878708, 0.0969652533531189, 0.07608342915773392, 0.17344005405902863, 0.1927212029695511, 0.17150157690048218, 0.12515395879745483, 0.7689521908760071, 0.9235615134239197, 0.5565314888954163, 0.721351146697998, 0.9718642234802246, 0.8328936696052551, 0.389932245016098, 0.32458633184432983, 0.5393264293670654, 0.7708479166030884, 1.0515438318252563, 0.40017226338386536, 0.6052955985069275, 1.2525968551635742, 1.2892076969146729, 0.4795728325843811, 0.7437009811401367, 0.3802849352359772, 0.8224507570266724, 1.2225592136383057, 0.33281251788139343, 0.6687111258506775, 0.4067545533180237, 0.5316631197929382, 0.760604977607727, 0.8714518547058105, 0.6217922568321228, 0.4113098084926605, 0.8672366142272949, 0.7891851663589478, 0.5323317050933838, 1.4271553754806519, 1.0884900093078613, 0.5799232125282288, 0.3412019908428192, 0.6966234445571899, 0.4183538854122162, 0.6835425496101379, 0.597611665725708, 0.7832285761833191, 0.6006167531013489, 0.6544936299324036, 0.5275521278381348, 1.0599753856658936, 0.56672203540802, 0.5278028249740601, 0.7443673014640808, 0.7104584574699402, 1.4316223859786987, 0.4958350360393524, 0.9246944785118103, 0.16106557846069336, 0.9449295401573181, 0.25429660081863403, 0.4466257095336914, 0.8181570172309875, 0.7001891136169434, 0.562343418598175, 0.36765173077583313, 0.7464469075202942, 0.5624530911445618, 0.6507547497749329, 0.9939277172088623, 0.3850487172603607, 0.5313770771026611, 0.6486282348632812, 0.7406859397888184, 0.8691455125808716, 0.5624632239341736, 1.2551133632659912, 1.0222277641296387, 0.2573477029800415, 0.8814558982849121, 0.6002023816108704, 1.169203758239746, 0.36656704545021057, 0.8371194005012512, 0.7861700057983398, 1.0058106184005737, 0.7576101422309875, 0.8052651286125183, 0.8722642064094543, 0.5067634582519531, 0.5916422605514526, 1.0624620914459229, 0.9322373270988464, 0.5497016310691833, 0.7287691235542297, 0.3558243215084076, 0.649656355381012, 0.9014331102371216, 0.8839743137359619, 0.3498522937297821, 1.0649707317352295, 0.5975762605667114, 0.8482107520103455, 0.5821531414985657, 0.9283477663993835, 0.7269198298454285, 0.8462626934051514, 0.6815134286880493, 0.3150752782821655, 0.8403915762901306, 0.5321004390716553, 0.14361608028411865, 0.5520085692405701, 0.620219886302948, 1.0009920597076416, 0.4681825637817383, 0.9934415221214294, 0.388784795999527, 0.4697688817977905, 0.8835356831550598, 0.5220698714256287, 0.33927902579307556, 0.6052853465080261, 1.2586557865142822, 0.5583146810531616, 1.0822046995162964, 0.3700013756752014, 0.6128862500190735, 0.4927752614021301, 0.6737831234931946, 0.5004578828811646, 0.9798011779785156, 1.0770113468170166, 0.46892988681793213, 0.46144118905067444, 0.9645898938179016, 0.551974356174469, 0.8041726350784302, 0.6398954391479492, 0.7808552980422974, 0.572358250617981, 1.006210446357727, 0.6546533107757568, 0.714028000831604, 0.8001077175140381, 0.6965168714523315, 0.6148629784584045, 0.3759787678718567, 0.7526748776435852, 0.6959770321846008, 0.3963707387447357, 0.5187437534332275, 0.8163407444953918, 0.8298953175544739, 0.7608566284179688, 0.7654836773872375, 0.9415032267570496, 0.5469310879707336, 0.7951823472976685, 0.40657752752304077, 0.619037926197052, 0.6085304021835327, 0.5695106983184814, 0.7738367915153503, 1.1154989004135132, 0.5756659507751465, 0.6963163614273071, 0.9714340567588806, 0.3811996877193451, 0.6685479879379272, 0.9521698355674744, 0.7394741773605347, 0.9068537950515747, 0.789078950881958, 0.9188982844352722, 0.8636357188224792, 0.4520317018032074, 0.27465346455574036, 0.43807145953178406, 0.4404829442501068, 0.9525855183601379, 0.9723910093307495, 0.6832543611526489, 0.5725545883178711, 0.37473493814468384, 0.5994107127189636, 1.0577138662338257, 0.4362184703350067, 0.5861964225769043, 0.5253380537033081, 1.1645196676254272, 1.1688599586486816, 0.9233091473579407, 0.3628219664096832, 1.1567763090133667, 0.4721764624118805, 1.25290846824646, 0.4454742968082428, 0.9365643262863159, 1.0926207304000854, 0.7775293588638306, 0.5045619606971741, 0.35639095306396484, 0.2479516863822937, 0.792386531829834, 0.9618433117866516, 0.45965704321861267, 0.8027157187461853, 0.3620058596134186, 1.0684176683425903, 0.3332495093345642, 1.4123650789260864, 0.7433646321296692, 0.6423512697219849, 1.1627790927886963, 0.3431870937347412, 0.7849336266517639, 0.6245781779289246, 0.3439878821372986, 0.39099350571632385, 0.4965783655643463, 0.9478971362113953, 0.8732150793075562, 0.6481756567955017, 0.5877474546432495, 0.9664681553840637, 0.4503897726535797, 0.6277209520339966, 0.861913800239563, 0.49957236647605896, 0.6972405314445496, 0.8924723863601685, 0.4537382125854492, 1.0830475091934204, 0.4490176737308502, 0.9359167218208313, 0.6527065634727478, 0.33733177185058594, 0.9415168762207031, 0.7137044072151184, 0.8040761947631836, 1.1996034383773804, 0.889950692653656, 0.4995613694190979, 0.810608983039856, 0.8365128636360168, 0.694269597530365, 1.0939910411834717, 0.4722352623939514, 0.8885806202888489, 1.0625593662261963, 0.7427079677581787, 1.1421679258346558, 0.31135404109954834, 0.5948792695999146, 0.8885390758514404, 0.8205550312995911, 0.6504727005958557, 0.6953580975532532, 0.768194854259491, 0.39580869674682617, 0.6857167482376099, 0.3426358699798584, 0.5548926591873169, 0.6060799360275269, 0.2073136419057846, 0.7061800956726074, 0.5948448777198792, 0.8146594166755676, 0.7104234099388123, 0.5008389949798584, 0.8479922413825989, 0.47256040573120117, 0.7248282432556152, 1.0207058191299438, 1.1037580966949463, 0.45646968483924866, 0.8586085438728333, 0.7112147212028503, 0.5971060991287231, 0.645522952079773, 0.5300540924072266, 0.7839817404747009, 0.8773191571235657, 0.5317529439926147, 0.5375620126724243, 1.063402771949768, 0.749724268913269, 0.7136373519897461, 0.7246983051300049, 1.0439425706863403, 0.34614208340644836, 0.7213905453681946, 0.47369909286499023, 0.6750327944755554, 0.4365144371986389, 0.3220910131931305, 0.42426925897598267, 1.093119740486145, 0.9398573040962219, 1.1576071977615356, 0.5871456861495972, 1.073982834815979, 0.2660371661186218, 0.7282465100288391, 0.6347724199295044, 0.4877358078956604, 32.329437255859375, 23.286834716796875, 100.71123504638672, 17.1214599609375, 14.906890869140625, 98.91068267822266, 81.88774871826172, 122.14276123046875, 38.80764389038086, 81.2490234375, 87.03694915771484, 63.92287826538086, 15.63207721710205, 83.332763671875, 30.747953414916992, 59.36121368408203, 78.99822998046875, 16.025543212890625, 77.55465698242188, 19.39599609375, 26.86286735534668, 95.54134368896484, 34.53981018066406, 75.57864379882812, 97.36504364013672, 125.8547592163086, 29.589935302734375, 114.37493896484375, 33.90510177612305, 16.996829986572266, 15.0419921875, 18.314910888671875, 35.96158218383789, 20.77623748779297, 52.85366439819336, 22.31022071838379, 118.64004516601562, 27.939430236816406, 27.380958557128906, 32.11802673339844, 10.900482177734375, 70.33983612060547, 26.632070541381836, 86.88170623779297, 69.28545379638672, 37.51780700683594, 54.59180450439453, 72.1426773071289, 22.41511344909668, 85.86886596679688, 57.60858154296875, 43.33064270019531, 59.57183837890625, 117.02533721923828, 56.849365234375, 127.43392181396484, 59.703182220458984, 115.00204467773438, 104.574462890625, 143.89559936523438, 55.600399017333984, 46.74953842163086, 21.040687561035156, 21.47930908203125, 79.35490417480469, 31.350555419921875, 43.6787109375, 13.29034423828125, 17.05034637451172, 19.70660400390625, 51.448211669921875, 35.66078186035156, 14.466459274291992, 57.867977142333984, 77.5663833618164, 14.247360229492188, 22.733671188354492, 32.13186264038086, 32.57923889160156, 24.578475952148438, 30.676483154296875, 23.354921340942383, 60.29998779296875, 91.5911636352539, 18.356658935546875, 27.326757431030273, 28.04129409790039, 51.29852294921875, 50.40571975708008, 13.11383056640625, 69.96131896972656, 46.38715744018555, 18.420379638671875, 52.276824951171875, 18.985158920288086, 71.56244659423828, 15.281508445739746, 41.733943939208984, 68.34809112548828, 27.973846435546875, 97.965087890625, 34.843475341796875, 153.96437072753906, 12.516677856445312, 91.77428436279297, 53.95143508911133, 37.836326599121094, 46.4134521484375, 34.34968566894531, 66.96768188476562, 37.667083740234375, 46.258460998535156, 52.21057891845703, 32.36442184448242, 123.457763671875, 47.914886474609375, 18.949920654296875, 45.379642486572266, 23.694915771484375, 11.803573608398438, 51.57688522338867, 32.56526184082031, 26.84454345703125, 108.14933013916016, 11.519694328308105, 46.75905990600586, 19.076995849609375, 36.64236068725586, 63.335205078125, 27.947601318359375, 89.49037170410156, 57.39895248413086, 53.5458984375, 67.26545715332031, 42.05125045776367, 33.95269775390625, 24.281234741210938, 136.44927978515625, 13.70135498046875, 48.61668395996094, 97.9109878540039, 43.430999755859375, 63.3048095703125, 106.92388153076172, 34.886592864990234, 25.167423248291016, 203.57872009277344, 28.775278091430664, 53.20130157470703, 37.69382095336914, 40.70002746582031, 39.21131896972656, 50.50293731689453, 50.045989990234375, 43.98004913330078, 58.13966751098633, 94.34435272216797, 18.670082092285156, 27.70782470703125, 19.776826858520508, 91.24571990966797, 75.0294189453125, 37.101776123046875, 47.00742721557617, 141.86154174804688, 39.72285842895508, 75.95626831054688, 75.56997680664062, 80.17582702636719, 54.0435791015625, 28.23994255065918, 34.94228744506836, 81.951416015625, 101.22832489013672, 24.947050094604492, 18.162736892700195, 14.171340942382812, 30.85479736328125, 34.52762222290039, 15.03924560546875, 84.07808685302734, 49.97141647338867, 21.071151733398438, 100.13802337646484, 49.326351165771484, 70.22576904296875, 33.61296081542969, 119.700927734375, 15.0235595703125, 46.597503662109375, 17.592071533203125, 73.82231903076172, 72.44021606445312, 39.98217010498047, 17.609647750854492, 45.6748046875, 53.67710876464844, 21.514102935791016, 77.9941177368164, 32.99058532714844, 63.40252685546875, 89.22295379638672, 9.590359687805176, 15.21728515625, 61.183929443359375, 40.0069580078125, 14.724273681640625, 116.1805419921875, 25.990224838256836, 52.64944076538086, 84.2197265625, 21.998886108398438, 69.70098114013672, 76.75634765625, 51.39162826538086, 78.28977966308594, 27.47991943359375, 44.849945068359375, 84.97085571289062, 55.86099624633789, 85.71998596191406, 26.70600700378418, 79.73342895507812, 31.27337646484375, 46.87920379638672, 34.83396911621094, 40.381317138671875, 68.72055053710938, 75.80213928222656, 73.27202606201172, 24.3199462890625, 78.86856079101562, 17.753524780273438, 19.530685424804688, 50.5947265625, 112.61492919921875, 28.155807495117188, 38.44921875, 13.16448974609375, 36.21915054321289, 14.275531768798828, 14.384261131286621, 18.119140625, 18.266664505004883, 42.4119873046875, 30.9656982421875, 52.559627532958984, 37.472900390625, 39.05495834350586, 112.7050552368164, 80.78401947021484, 48.90611267089844, 29.772979736328125, 60.818450927734375, 22.73675537109375, 126.0511474609375, 246.4901580810547, 64.18939208984375, 23.098495483398438, 92.01089477539062, 31.569843292236328, 57.89997863769531, 20.0, 63.38412857055664, 129.67532348632812, 49.99734115600586, 38.62302017211914, 78.11932373046875, 22.003021240234375, 61.48202133178711, 54.7050666809082, 28.41946792602539, 43.711483001708984, 47.965301513671875, 26.19268798828125, 42.590545654296875, 17.12249755859375, 23.854887008666992, 18.622955322265625, 130.510498046875, 92.6990966796875, 48.92529296875, 93.19893646240234, 121.706298828125, 27.315841674804688, 67.11347198486328, 21.50387191772461, 16.553802490234375, 51.21097183227539, 13.125089645385742, 45.77444076538086, 121.54371643066406, 57.054534912109375, 79.21817016601562, 38.25981903076172, 15.431427001953125, 38.15372085571289, 42.8656005859375, 43.512977600097656, 23.048105239868164, 2.6913580894470215, 2.778693437576294, 2.0829312801361084, 2.063858985900879, 1.809578776359558, 1.952967643737793, 2.4807310104370117, 2.566850423812866, 1.2883360385894775, 1.9129958152770996, 1.9246997833251953, 2.107639789581299, 2.916487455368042, 2.9641520977020264, 2.5439233779907227, 1.8430514335632324, 2.659219980239868, 3.3466851711273193, 1.8397141695022583, 1.84346342086792, 1.2484455108642578, 2.6073553562164307, 2.771554470062256, 1.1114274263381958, 2.328152656555176, 1.3833377361297607, 2.991441011428833, 1.911852240562439, 1.9637001752853394, 3.1101531982421875, 1.7129334211349487, 2.5403895378112793, 1.8209905624389648, 1.8974218368530273, 1.987174391746521, 1.9126601219177246, 2.0510311126708984, 1.2254785299301147, 1.7305649518966675, 1.048237681388855, 1.1505117416381836, 2.163525104522705, 3.036330461502075, 2.517996072769165, 2.361222743988037, 2.4808876514434814, 1.9226349592208862, 1.469618797302246, 2.8677313327789307, 2.598273277282715, 2.050877094268799, 1.997538685798645, 1.7905492782592773, 2.707049608230591, 3.0462863445281982, 2.385674476623535, 1.4820501804351807, 2.780850648880005, 2.422424554824829, 1.833729863166809, 2.1597108840942383, 3.680353879928589, 1.5383062362670898, 2.1289100646972656, 2.6170403957366943, 1.8266609907150269, 2.162259101867676, 1.7579964399337769, 1.606562614440918, 2.2798962593078613, 2.2651212215423584, 2.396989107131958, 2.3012425899505615, 1.3954180479049683, 1.359601378440857, 3.8639214038848877, 1.7623586654663086, 2.38550066947937, 2.767016887664795, 2.109084367752075, 1.1798104047775269, 2.352353572845459, 2.1873419284820557, 3.2371304035186768, 1.8463174104690552, 2.359360694885254, 1.7736730575561523, 1.3822355270385742, 1.4500014781951904, 2.5707526206970215, 1.4806145429611206, 2.975560426712036, 2.8794610500335693, 1.8656682968139648, 2.047945976257324, 1.847902536392212, 1.973646640777588, 2.4228622913360596, 2.1117775440216064, 1.7953063249588013, 1.7554372549057007, 2.9134130477905273, 1.1951000690460205, 1.5110212564468384, 2.0425162315368652, 1.6220749616622925, 1.7457913160324097, 2.0070302486419678, 2.689310312271118, 2.9282138347625732, 3.222414970397949, 2.652421236038208, 2.624699592590332, 1.5763158798217773, 2.1133031845092773, 3.3063840866088867, 1.5490657091140747, 1.966103196144104, 2.3972809314727783, 2.5683887004852295, 2.034665107727051, 2.040786027908325, 2.7597618103027344, 2.3879714012145996, 2.352332592010498, 2.2088518142700195, 1.4036898612976074, 2.3510262966156006, 2.591550350189209, 2.349862813949585, 1.9872770309448242, 1.6647748947143555, 2.274235248565674, 2.4551494121551514, 2.4057607650756836, 2.1655848026275635, 2.9446916580200195, 1.748834490776062, 1.8397094011306763, 1.9603241682052612, 1.715962290763855, 3.3694562911987305, 2.605001449584961, 2.1823532581329346, 2.4612197875976562, 1.9606479406356812, 1.5100334882736206, 1.339716911315918, 1.7499133348464966, 1.6858313083648682, 2.7501842975616455, 2.545407295227051, 1.4044908285140991, 1.7790145874023438, 1.940995454788208, 1.3350069522857666, 1.778497576713562, 2.1632070541381836, 3.6298766136169434, 1.3167104721069336, 1.626460075378418, 1.3058441877365112, 2.556361436843872, 2.287750244140625, 1.8523588180541992, 1.548670768737793, 1.575508952140808, 1.3136777877807617, 1.3714525699615479, 1.8023159503936768, 1.7517659664154053, 1.7912660837173462, 2.2951152324676514, 2.4520838260650635, 2.99039363861084, 1.7033501863479614, 1.315669059753418, 2.6424572467803955, 1.626412272453308, 2.32034969329834, 2.900761604309082, 2.1330978870391846, 1.4948266744613647, 1.8715029954910278, 2.7995007038116455, 1.438934326171875, 2.120112419128418, 3.380269765853882, 3.0064775943756104, 2.436223268508911, 1.6526192426681519, 1.9794111251831055, 2.3965463638305664, 1.3845185041427612, 2.209477424621582, 2.2572736740112305, 2.2565383911132812, 1.9942291975021362, 1.9620484113693237, 1.2312554121017456, 1.5610134601593018, 2.1489040851593018, 1.1882781982421875, 2.522250175476074, 2.0410022735595703, 1.700518012046814, 1.6449689865112305, 2.0050668716430664, 2.2386627197265625, 2.5884740352630615, 2.7693235874176025, 3.173499584197998, 2.4473443031311035, 3.107935667037964, 1.8015618324279785, 2.1292314529418945, 1.5120590925216675, 1.4583098888397217, 2.5333685874938965, 3.445356607437134, 2.0288383960723877, 1.9793401956558228, 3.169140577316284, 2.3561792373657227, 2.431380271911621, 2.686077117919922, 2.957155704498291, 2.218874931335449, 1.3276934623718262, 3.6315391063690186, 2.0768606662750244, 1.5012561082839966, 1.437178611755371, 1.2959686517715454, 1.2676118612289429, 2.8725602626800537, 1.609248161315918, 2.9301652908325195, 2.018710136413574, 1.293593406677246, 0.9632043242454529, 1.7406682968139648, 1.8271795511245728, 1.4696804285049438, 1.358302116394043, 2.159661293029785, 1.813812255859375, 1.7468994855880737, 1.8133400678634644, 2.6522533893585205, 2.2452402114868164, 3.0366411209106445, 2.608179807662964, 1.8589938879013062, 3.644207715988159, 1.5875005722045898, 2.534602165222168, 1.6529440879821777, 2.0665578842163086, 2.1090049743652344, 1.9195855855941772, 2.133845329284668, 1.6891201734542847, 1.1786240339279175, 1.3420952558517456, 2.4195094108581543, 1.799530029296875, 1.8963974714279175, 3.0224273204803467, 2.861542224884033, 2.0745906829833984, 2.1220734119415283, 1.9698500633239746, 2.3021230697631836, 1.7678273916244507, 1.734803557395935, 2.838430166244507, 3.0532867908477783, 3.270458221435547, 1.8820226192474365, 1.3740034103393555, 1.605322241783142, 1.6615722179412842, 2.1072378158569336, 1.667866587638855, 2.147531270980835, 1.6756768226623535, 2.763784170150757, 1.8124363422393799, 2.361630439758301, 2.44674015045166, 2.1678152084350586, 2.4127981662750244, 1.8821325302124023, 1.4534802436828613, 2.8712542057037354, 2.315789222717285, 1.893568992614746, 2.3488335609436035, 2.130192756652832, 0.03958481550216675, 0.05385961756110191, 0.12726786732673645, 0.08177324384450912, 0.11569435149431229, 0.054458752274513245, 0.1044062003493309, 0.09287776052951813, 0.08854246884584427, 0.1551729291677475, 0.13681043684482574, 0.04653966799378395, 0.1766391098499298, 0.14358234405517578, 0.09549485892057419, 0.11656954139471054, 0.07655365020036697, 0.0982707217335701, 0.12181632965803146, 0.12937143445014954, 0.11736281961202621, 0.12486809492111206, 0.10261557251214981, 0.04076715558767319, 0.04245283082127571, 0.1487334966659546, 0.06482638418674469, 0.03244274482131004, 0.05212008208036423, 0.1142377257347107, 0.04456440731883049, 0.13159894943237305, 0.13424256443977356, 0.12182071059942245, 0.08852852880954742, 0.04002140834927559, 0.12241490930318832, 0.13535042107105255, 0.14659249782562256, 0.12359818816184998, 0.1009371280670166, 0.06648478657007217, 0.05524831265211105, 0.1110931783914566, 0.10295239835977554, 0.1481378972530365, 0.06662900000810623, 0.11474794149398804, 0.15832257270812988, 0.09687706083059311, 0.07275562733411789, 0.14786767959594727, 0.1444348692893982, 0.1006600558757782, 0.10481330007314682, 0.08436036109924316, 0.12195909023284912, 0.16662395000457764, 0.09387385845184326, 0.05254049971699715, 0.08799352496862411, 0.07677184045314789, 0.1573392003774643, 0.06594337522983551, 0.10264717787504196, 0.08890485763549805, 0.12980270385742188, 0.16514858603477478, 0.2076047658920288, 0.1059383749961853, 0.13967472314834595, 0.11946717649698257, 0.09502357244491577, 0.11498653888702393, 0.1724938154220581, 0.07845216244459152, 0.04929627478122711, 0.10727691650390625, 0.09121644496917725, 0.06664233654737473, 0.12736333906650543, 0.13258910179138184, 0.08784952014684677, 0.09951211512088776, 0.03825255110859871, 0.08745976537466049, 0.15015989542007446, 0.07026445865631104, 0.1737983226776123, 0.0909859836101532, 0.10393992811441422, 0.08480079472064972, 0.08093544840812683, 0.06993133574724197, 0.14708010852336884, 0.06204570457339287, 0.13811896741390228, 0.05123697966337204, 0.14815986156463623, 0.15367454290390015, 0.1843523532152176, 0.11404432356357574, 0.10122096538543701, 0.1644742488861084, 0.11822070926427841, 0.06528142839670181, 0.11406958103179932, 0.0825386568903923, 0.11867231875658035, 0.1003674864768982, 0.08589372783899307, 0.05919216200709343, 0.11741260439157486, 0.153102844953537, 0.10842280834913254, 0.09871954470872879, 0.11280941963195801, 0.07937929034233093, 0.15412470698356628, 0.11269202083349228, 0.06633591651916504, 0.15312793850898743, 0.11232711374759674, 0.13441525399684906, 0.055944595485925674, 0.13097065687179565, 0.09929507970809937, 0.10318692773580551, 0.196553036570549, 0.06757239252328873, 0.08205380290746689, 0.08575795590877533, 0.10685083270072937, 0.09234791249036789, 0.12235098332166672, 0.10264529287815094, 0.157373309135437, 0.1359184980392456, 0.055881381034851074, 0.028614753857254982, 0.10555839538574219, 0.1407277137041092, 0.09806234389543533, 0.12891757488250732, 0.10804087668657303, 0.14786916971206665, 0.15146636962890625, 0.09426969289779663, 0.1646934151649475, 0.09178036451339722, 0.11421088874340057, 0.08490884304046631, 0.09595334529876709, 0.15196602046489716, 0.13270394504070282, 0.11596710979938507, 0.15084055066108704, 0.04813389852643013, 0.09942338615655899, 0.16800396144390106, 0.13859044015407562, 0.09455861896276474, 0.09013479948043823, 0.10857963562011719, 0.11458778381347656, 0.11732374876737595, 0.20191390812397003, 0.08051256835460663, 0.0370476134121418, 0.03595777601003647, 0.12820802628993988, 0.0759580135345459, 0.12692175805568695, 0.09160792082548141, 0.12844456732273102, 0.004876831546425819, 0.058894719928503036, 0.035464223474264145, 0.11929281055927277, 0.2091495394706726, 0.1285756379365921, 0.06382899731397629, 0.11376754194498062, 0.11220912635326385, 0.12090040743350983, 0.11166152358055115, 0.08395039290189743, 0.06323665380477905, 0.06712337583303452, 0.04764242470264435, 0.16214460134506226, 0.10485425591468811, 0.0935291275382042, 0.20596885681152344, 0.11082843691110611, 0.092022605240345, 0.1400594264268875, 0.11757092922925949, 0.15977025032043457, 0.11968275904655457, 0.0996408611536026, 0.08573052287101746, 0.14114581048488617, 0.083770751953125, 0.14013725519180298, 0.06871980428695679, 0.1288900375366211, 0.0731910839676857, 0.12851248681545258, 0.14241021871566772, 0.1348782181739807, 0.14474068582057953, 0.07218671590089798, 0.107474684715271, 0.11653760820627213, 0.09210838377475739, 0.08393628895282745, 0.10014313459396362, 0.05156170576810837, 0.11883405596017838, 0.14632642269134521, 0.15486599504947662, 0.15123966336250305, 0.10560836642980576, 0.0670647919178009, 0.08186514675617218, 0.10261180996894836, 0.12807656824588776, 0.0954047366976738, 0.08948072046041489, 0.13548825681209564, 0.14262348413467407, 0.10096925497055054, 0.07926935702562332, 0.10564613342285156, 0.16840286552906036, 0.1501207947731018, 0.04516761749982834, 0.13492907583713531, 0.16024401783943176, 0.06539983302354813, 0.14791801571846008, 0.05674179270863533, 0.09176594763994217, 0.06938272714614868, 0.08083166182041168, 0.2226315289735794, 0.19589464366436005, 0.08924371749162674, 0.07069987058639526, 0.10409919172525406, 0.10668469220399857, 0.07272367924451828, 0.12340719252824783, 0.07238008081912994, 0.11372240632772446, 0.09091373533010483, 0.0915185734629631, 0.09968011826276779, 0.14098334312438965, 0.028537068516016006, 0.099094457924366, 0.1196797713637352, 0.10667645931243896, 0.12298803776502609, 0.07449035346508026, 0.10045433044433594, 0.11974597722291946, 0.10048013180494308, 0.14336486160755157, 0.08552339673042297, 0.16256122291088104, 0.05444290116429329, 0.1246294379234314, 0.11342906951904297, 0.10270147770643234, 0.0772056132555008, 0.08986866474151611, 0.12669391930103302, 0.1776573657989502, 0.14373072981834412, 0.08439387381076813, 0.12835770845413208, 0.1748080551624298, 0.08539026975631714, 0.11182571202516556, 0.10954133421182632, 0.08373159170150757, 0.053093280643224716, 0.11997878551483154, 0.15135683119297028, 0.0678369328379631, 0.0798719972372055, 0.06721831113100052, 0.06532876193523407, 0.17175798118114471, 0.12060650438070297, 0.06551436334848404, 0.07532763481140137, 0.123661570250988, 0.4609167277812958, 0.6221343278884888, 0.19856643676757812, 0.8752482533454895, 0.5052054524421692, 0.6188281774520874, 0.3656342327594757, 0.5089153051376343, 0.8357373476028442, 0.46400076150894165, 0.3316766619682312, 0.574708878993988, 0.7633801698684692, 0.6023180484771729, 1.209790825843811, 0.43760618567466736, 1.0092097520828247, 0.6157463192939758, 0.28663185238838196, 0.7451360821723938, 0.5212911367416382, 0.7170854806900024, 0.5606882572174072, 0.8487809300422668, 0.8060540556907654, 0.9452566504478455, 0.8451366424560547, 0.27258017659187317, 0.5248811841011047, 0.44057169556617737, 1.0854798555374146, 1.1391422748565674, 0.5257648229598999, 0.8122628331184387, 0.7346431612968445, 0.331815630197525, 0.2723614573478699, 0.7257639169692993, 0.6701523661613464, 0.3964858949184418, 0.4844864308834076, 0.8246581554412842, 0.3165423274040222, 0.6222440004348755, 0.5017040967941284, 0.2086576223373413, 0.7556690573692322, 0.5000214576721191, 0.9149694442749023, 0.5318615436553955, 1.121371865272522, 1.2377393245697021, 0.7155078053474426, 0.733969509601593, 0.7363919019699097, 0.6326330304145813, 0.32663601636886597, 0.6984378099441528, 0.40979665517807007, 0.7647215127944946, 0.4698947072029114, 0.5252959728240967, 0.993466854095459, 0.5400518178939819, 0.5790125727653503, 1.0067992210388184, 0.6799212694168091, 0.8038075566291809, 0.6397820711135864, 0.7846819758415222, 0.40668952465057373, 0.4552776515483856, 0.7202227711677551, 1.3583338260650635, 0.3313767910003662, 0.7746391296386719, 0.8387881517410278, 0.6279314756393433, 1.0106227397918701, 0.4677446782588959, 0.9638584852218628, 0.35301047563552856, 0.7624768018722534, 0.2742407023906708, 0.9370409846305847, 1.256594181060791, 0.8868487477302551, 0.6699810028076172, 0.4813837707042694, 1.4908291101455688, 0.6129237413406372, 0.5169569849967957, 0.8325806856155396, 0.4753533899784088, 1.1080914735794067, 0.5946070551872253, 1.1889212131500244, 1.030609369277954, 0.3793790340423584, 0.6794949769973755, 0.9155072569847107, 1.3248056173324585, 0.41470587253570557, 0.5652986764907837, 0.579055905342102, 0.9906613230705261, 0.485984206199646, 0.6507444381713867, 0.29194381833076477, 0.505240797996521, 0.6227978467941284, 0.6196471452713013, 0.5376443862915039, 0.5533708333969116, 0.5935375690460205, 0.9911567568778992, 0.9705880284309387, 1.366125464439392, 1.090423583984375, 0.8260951042175293, 0.3530258238315582, 0.7194140553474426, 0.7484471201896667, 0.6919997334480286, 0.8885149955749512, 0.7624489665031433, 0.7299859523773193, 0.5427245497703552, 0.9655811786651611, 1.0801594257354736, 0.5047200322151184, 0.7434824109077454, 0.8884642720222473, 0.517370343208313, 0.7204707264900208, 0.29468655586242676, 0.444446325302124, 0.891236424446106, 0.8877975344657898, 0.4490344524383545, 0.9257996082305908, 0.523814857006073, 0.24589045345783234, 0.5953812003135681, 0.834948718547821, 0.6855512857437134, 0.6479557752609253, 0.6555141806602478, 0.48318561911582947, 0.4009020924568176, 0.826295018196106, 1.1626369953155518, 0.7870835661888123, 1.2356605529785156, 0.70191890001297, 0.2514715790748596, 0.4736231863498688, 1.3521640300750732, 0.7342866063117981, 0.47828778624534607, 0.9909716844558716, 0.7917842864990234, 0.8126605153083801, 0.6256020665168762, 0.7894819378852844, 0.7958568930625916, 1.1397838592529297, 0.5737372636795044, 0.918251097202301, 0.5755196213722229, 0.5376578569412231, 0.6076582074165344, 1.154239296913147, 0.6511390805244446, 0.7139879465103149, 0.18830043077468872, 0.22047625482082367, 0.5922582745552063, 1.0918844938278198, 0.6982860565185547, 0.7655060887336731, 0.8428705334663391, 0.803095817565918, 0.5993983149528503, 0.391683429479599, 0.9643538594245911, 1.1451700925827026, 0.9559155702590942, 0.9755390882492065, 0.8481125235557556, 0.9947379231452942, 0.785084068775177, 0.7679582834243774, 0.9688766002655029, 1.034149408340454, 0.5857790112495422, 0.7137885689735413, 0.5227469801902771, 0.6300538182258606, 0.7109867930412292, 1.196442723274231, 0.8040780425071716, 0.5219349265098572, 0.9415913820266724, 0.4304516911506653, 0.8500514030456543, 0.6125867962837219, 1.2957751750946045, 1.3469021320343018, 0.571421205997467, 1.0465670824050903, 0.851581871509552, 0.7861202955245972, 0.9565312266349792, 0.8458130955696106, 0.6959025263786316, 0.9183679819107056, 0.4919850826263428, 0.820124089717865, 0.7140137553215027, 0.6275421977043152, 0.404060423374176, 0.7246876955032349, 1.113407015800476, 0.4790074825286865, 0.48149362206459045, 0.6454820036888123, 0.5232954025268555, 1.0030910968780518, 0.33052635192871094, 0.641444981098175, 0.8231694102287292, 0.7978203892707825, 0.951231837272644, 0.8895477652549744, 1.029510498046875, 0.8882739543914795, 0.8567482829093933, 0.8282296061515808, 0.6472855806350708, 0.7634463310241699, 0.5897814631462097, 0.9293192028999329, 0.5971899032592773, 0.2941758334636688, 0.9951772689819336, 0.7518308758735657, 0.9191451072692871, 0.46003657579421997, 0.5699613094329834, 0.6664959788322449, 0.5302053093910217, 0.3508996367454529, 0.5363405346870422, 0.8083908557891846, 0.7576452493667603, 0.3401028513908386, 0.5499252676963806, 0.5276190042495728, 0.39448466897010803, 0.49075010418891907, 0.8597349524497986, 0.8962915539741516, 0.5035479664802551, 1.2464722394943237, 0.8365141153335571, 0.6964913010597229, 0.4132060110569, 0.47519439458847046, 0.5628361105918884, 0.8573112487792969, 0.5086148977279663, 0.4848337173461914, 0.6326995491981506, 0.7285418510437012, 0.6132064461708069, 0.8150537014007568, 0.5177925229072571, 0.8896152973175049, 1.330181360244751, 0.6791448593139648, 0.7061376571655273, 0.5145075917243958, 0.5178733468055725, 0.544182538986206, 0.7842808365821838, 0.9512754082679749, 0.9822949171066284, 0.8668605089187622, 0.8180769085884094, 0.8496562242507935, 0.8740360736846924, 0.7748910188674927, 1.027718186378479, 0.8443723917007446, 0.8461162447929382, 0.49508365988731384, 0.3972903788089752, 0.5558046102523804, 0.6785643100738525, 13.53271484375, 15.8726806640625, 70.2421646118164, 78.92178344726562, 122.33150482177734, 53.825008392333984, 60.02337646484375, 28.869476318359375, 19.18228530883789, 35.676116943359375, 42.46047592163086, 54.11030960083008, 16.809274673461914, 23.194169998168945, 101.26025390625, 85.36553192138672, 25.3702392578125, 41.891326904296875, 89.9810562133789, 75.7983169555664, 23.320829391479492, 63.36066818237305, 26.6658935546875, 60.513240814208984, 55.63380813598633, 26.60687255859375, 121.78179168701172, 70.207763671875, 39.52773666381836, 77.71953582763672, 63.52402114868164, 28.517187118530273, 22.1854248046875, 32.42352294921875, 159.16421508789062, 124.71662139892578, 49.567596435546875, 36.02275466918945, 135.69876098632812, 66.25369262695312, 69.84319305419922, 40.33266830444336, 92.55992126464844, 68.044677734375, 24.789794921875, 26.49107551574707, 54.471435546875, 118.53549194335938, 14.290924072265625, 26.437894821166992, 28.2095947265625, 17.698028564453125, 31.581327438354492, 29.075136184692383, 29.012470245361328, 13.85488510131836, 19.030080795288086, 166.5843963623047, 16.616180419921875, 63.138450622558594, 58.01605224609375, 47.99489974975586, 60.67238998413086, 68.61531066894531, 26.79852294921875, 24.916961669921875, 42.232025146484375, 43.828182220458984, 60.98095703125, 33.69519805908203, 48.5494384765625, 16.680784225463867, 70.5528564453125, 33.750213623046875, 14.950286865234375, 50.6044921875, 69.58987426757812, 11.288070678710938, 17.289276123046875, 34.352840423583984, 141.64549255371094, 40.002288818359375, 36.204193115234375, 180.25901794433594, 35.41026306152344, 26.63177490234375, 46.438270568847656, 108.15447998046875, 147.17745971679688, 21.298662185668945, 155.2640380859375, 39.354576110839844, 27.756826400756836, 53.06399154663086, 46.0832405090332, 40.81931686401367, 29.6151123046875, 98.2806625366211, 185.1791229248047, 31.6361083984375, 73.14297485351562, 21.218814849853516, 14.804595947265625, 47.27836227416992, 40.32888412475586, 111.31997680664062, 55.08138656616211, 119.86429595947266, 84.82568359375, 59.424354553222656, 58.242889404296875, 42.216400146484375, 44.1109619140625, 90.82125091552734, 68.07144165039062, 40.711517333984375, 69.1504898071289, 110.509033203125, 82.9495849609375, 64.48989868164062, 67.76786041259766, 52.7479248046875, 47.372802734375, 16.90162467956543, 65.26142883300781, 30.141891479492188, 93.7144546508789, 73.9093017578125, 21.342529296875, 31.036468505859375, 15.997255325317383, 73.85659790039062, 27.497684478759766, 87.95671081542969, 41.44590377807617, 108.56011199951172, 65.6904067993164, 85.08377838134766, 55.57489013671875, 37.23126220703125, 23.425443649291992, 53.38161087036133, 30.15174674987793, 175.86929321289062, 39.79189682006836, 48.98268508911133, 92.61929321289062, 21.09698486328125, 36.30532455444336, 15.098068237304688, 41.747772216796875, 19.475309371948242, 61.720027923583984, 44.592586517333984, 16.406005859375, 84.1024398803711, 63.32624435424805, 35.9029541015625, 60.4582633972168, 43.823265075683594, 153.01931762695312, 83.64458465576172, 77.91487884521484, 34.76359558105469, 23.172391891479492, 42.08973693847656, 35.26298141479492, 51.302093505859375, 12.063615798950195, 149.38101196289062, 24.70071792602539, 37.61794662475586, 42.9628791809082, 28.527069091796875, 59.8017578125, 83.06163787841797, 40.57101821899414, 63.3747444152832, 87.40591430664062, 19.673797607421875, 41.2549934387207, 94.994140625, 71.62893676757812, 22.991703033447266, 92.15444946289062, 23.419504165649414, 19.153839111328125, 47.315673828125, 80.97413635253906, 30.48994255065918, 28.900625228881836, 59.838470458984375, 45.9047737121582, 56.459617614746094, 32.77459716796875, 85.00257873535156, 89.26171875, 126.03042602539062, 62.58423614501953, 37.48748779296875, 23.73974609375, 28.503246307373047, 24.27457046508789, 72.09217071533203, 137.78009033203125, 9.08123779296875, 43.111366271972656, 26.432790756225586, 260.90655517578125, 124.93939208984375, 58.64382553100586, 262.0555725097656, 23.146453857421875, 134.76048278808594, 64.31219482421875, 17.2374267578125, 62.65179443359375, 19.57257080078125, 28.462203979492188, 28.400165557861328, 72.12496948242188, 43.57291030883789, 141.60809326171875, 22.834829330444336, 52.554046630859375, 52.15501022338867, 23.820968627929688, 93.3428726196289, 68.00991821289062, 59.34307098388672, 39.93206787109375, 82.0682601928711, 41.82118225097656, 19.160003662109375, 31.68695068359375, 38.15888214111328, 36.3189697265625, 29.332948684692383, 99.1282958984375, 37.72646713256836, 46.30626678466797, 18.663055419921875, 45.48681640625, 19.05426025390625, 46.05250930786133, 19.085845947265625, 58.963680267333984, 57.31850814819336, 15.790496826171875, 19.70306396484375, 30.48516845703125, 197.850341796875, 34.84860610961914, 36.83596420288086, 37.76795959472656, 32.8118896484375, 63.832763671875, 79.51312255859375, 57.92130661010742, 48.96015167236328, 33.106170654296875, 33.89541244506836, 28.562040328979492, 124.529052734375, 39.95559310913086, 53.95623779296875, 63.59626770019531, 42.95989990234375, 38.33120346069336, 59.57427978515625, 113.65496826171875, 112.20919799804688, 30.868392944335938, 91.9225082397461, 32.10126876831055, 20.3593807220459, 52.31667709350586, 14.344069480895996, 45.55266571044922, 17.164077758789062, 27.36343002319336, 51.3643798828125, 222.625, 53.78495788574219, 25.976043701171875, 85.69343566894531, 70.87277221679688, 54.986141204833984, 116.01019287109375, 81.91635131835938, 24.095243453979492, 77.20352172851562, 42.03015899658203, 95.1180648803711, 48.04580307006836, 35.264564514160156, 54.53213119506836, 13.018051147460938, 12.369285583496094, 13.29986572265625, 2.3717663288116455, 2.364407539367676, 2.889115571975708, 2.62691593170166, 2.023867607116699, 2.5014636516571045, 1.0357983112335205, 1.5038882493972778, 1.8241015672683716, 1.8965805768966675, 2.0586178302764893, 3.1953532695770264, 1.9759325981140137, 2.588344097137451, 3.447331428527832, 1.9465850591659546, 2.0345282554626465, 2.791081428527832, 2.3940999507904053, 2.329895496368408, 1.762807011604309, 2.1741456985473633, 2.093782424926758, 1.6983680725097656, 2.235781669616699, 2.0821218490600586, 1.5394420623779297, 2.592848777770996, 2.583538770675659, 2.674387216567993, 2.1519651412963867, 1.69813072681427, 2.4663357734680176, 2.0740292072296143, 2.0423059463500977, 1.5582189559936523, 1.4961544275283813, 1.218409538269043, 2.405402183532715, 1.762542724609375, 1.9305181503295898, 1.8607442378997803, 2.550710439682007, 2.3324007987976074, 1.5807174444198608, 2.3080053329467773, 2.0423707962036133, 3.1507678031921387, 3.6833572387695312, 2.37125301361084, 1.767743468284607, 1.2933624982833862, 1.8552219867706299, 3.3656437397003174, 2.826411724090576, 2.54707670211792, 1.7287453413009644, 2.5157673358917236, 2.0615968704223633, 3.325413227081299, 1.4872735738754272, 1.9008879661560059, 2.7224647998809814, 1.4584230184555054, 2.4527511596679688, 2.099806785583496, 3.2692630290985107, 2.6078364849090576, 2.5795085430145264, 3.292973518371582, 2.725071430206299, 2.4833407402038574, 2.553173303604126, 2.3433732986450195, 2.613011360168457, 3.2002415657043457, 1.5182209014892578, 1.4768129587173462, 1.8157596588134766, 1.9052164554595947, 1.9781793355941772, 2.6202709674835205, 1.4368231296539307, 1.2215306758880615, 2.333677053451538, 1.3048523664474487, 2.0674238204956055, 2.537503242492676, 2.6105635166168213, 1.2998876571655273, 2.657316207885742, 2.994685411453247, 2.319380760192871, 1.5486952066421509, 2.2741942405700684, 1.7931089401245117, 2.552119255065918, 2.3605220317840576, 2.0490217208862305, 2.1807353496551514, 2.358179807662964, 1.40632164478302, 1.60572350025177, 2.4570932388305664, 2.9109508991241455, 1.4275991916656494, 1.8142943382263184, 2.1114418506622314, 3.594906806945801, 3.552375078201294, 2.1055569648742676, 2.4861035346984863, 1.5859674215316772, 1.7767467498779297, 2.1293141841888428, 2.4571006298065186, 2.2980754375457764, 2.408215284347534, 1.651162028312683, 3.188645601272583, 2.2122037410736084, 2.9111785888671875, 2.452995538711548, 3.056652069091797, 2.526867628097534, 2.3009469509124756, 1.9875750541687012, 3.0095129013061523, 1.3442342281341553, 1.8993371725082397, 2.3087399005889893, 1.5343623161315918, 1.319441795349121, 2.442286252975464, 2.2353062629699707, 1.6366920471191406, 1.6635780334472656, 2.6687445640563965, 2.445038318634033, 2.3117010593414307, 1.7628965377807617, 2.8900890350341797, 1.868947148323059, 2.8123087882995605, 3.006788969039917, 2.25777530670166, 2.2827162742614746, 1.7221441268920898, 2.5922131538391113, 2.289578914642334, 2.0768136978149414, 1.823878288269043, 1.8680123090744019, 2.810126781463623, 2.2244298458099365, 2.494379997253418, 1.4062414169311523, 2.886715888977051, 1.8720312118530273, 2.5788042545318604, 1.3963006734848022, 1.9397077560424805, 1.7004668712615967, 1.8851290941238403, 2.5388593673706055, 2.2248992919921875, 3.8599631786346436, 1.1364507675170898, 1.9517015218734741, 2.3730196952819824, 2.5303847789764404, 1.3963901996612549, 2.8088388442993164, 2.542536735534668, 1.5030910968780518, 1.6329706907272339, 1.4202343225479126, 2.289336681365967, 2.550564765930176, 2.3819081783294678, 1.5766597986221313, 1.5340173244476318, 1.8704028129577637, 2.257286310195923, 1.6842939853668213, 2.0690345764160156, 1.2713232040405273, 3.003068208694458, 1.8667755126953125, 2.916470766067505, 2.1804323196411133, 1.6614866256713867, 2.1086442470550537, 1.2417672872543335, 1.0691862106323242, 2.288825035095215, 1.8275951147079468, 1.1913732290267944, 3.168337345123291, 1.379769206047058, 2.0879554748535156, 1.496171236038208, 2.1631429195404053, 1.4228445291519165, 2.5832338333129883, 2.4076149463653564, 2.5814645290374756, 1.3311741352081299, 2.3285984992980957, 2.506037712097168, 1.8093713521957397, 2.05783748626709, 0.8282427191734314, 2.780932664871216, 1.772597312927246, 2.893418550491333, 3.0529415607452393, 2.369215726852417, 1.6316841840744019, 1.6632076501846313, 1.1150237321853638, 2.2215545177459717, 2.0639848709106445, 1.783020257949829, 1.8843865394592285, 1.2462643384933472, 2.762195348739624, 1.6180716753005981, 1.4378265142440796, 2.3877103328704834, 3.358712911605835, 2.5006887912750244, 2.5340070724487305, 2.7782704830169678, 2.8812577724456787, 1.365767478942871, 2.342224597930908, 2.3946614265441895, 1.6438350677490234, 2.2367360591888428, 1.7322518825531006, 2.560093879699707, 1.6478550434112549, 2.540872812271118, 2.0844717025756836, 1.7263647317886353, 2.667335033416748, 1.8266537189483643, 1.2356786727905273, 2.507741928100586, 1.7195534706115723, 2.640948534011841, 3.003995895385742, 1.6092766523361206, 2.010577440261841, 2.3998756408691406, 2.2171013355255127, 2.109739303588867, 1.5539809465408325, 3.0728161334991455, 1.875631332397461, 2.5657026767730713, 1.9766665697097778, 1.8071823120117188, 3.16495680809021, 2.002520799636841, 1.461739420890808, 2.0262696743011475, 1.6858935356140137, 1.1197929382324219, 2.4910635948181152, 2.4338979721069336, 2.520564079284668, 2.2494611740112305, 2.169816017150879, 1.5984667539596558, 2.9750213623046875, 1.7300630807876587, 1.3437470197677612, 2.66288685798645, 1.3288506269454956, 1.2439510822296143, 2.466761589050293, 1.5620136260986328, 1.9256850481033325, 1.446059226989746, 1.4458733797073364, 2.25480318069458, 2.104098320007324, 2.634272336959839, 1.2549467086791992, 1.289483904838562, 1.6637150049209595, 2.232671022415161, 1.7583893537521362, 1.874221920967102, 2.0990114212036133, 2.1118407249450684, 2.220757484436035, 2.9079928398132324, 0.09664753079414368, 0.1479475498199463, 0.07465115189552307, 0.17857152223587036, 0.17427116632461548, 0.13075119256973267, 0.04331858456134796, 0.17554457485675812, 0.09331332892179489, 0.11021288484334946, 0.06435851007699966, 0.0862833559513092, 0.09137879312038422, 0.1719241440296173, 0.08842163532972336, 0.128614604473114, 0.10495216399431229, 0.15355505049228668, 0.06425688415765762, 0.09434536099433899, 0.05855807289481163, 0.14183840155601501, 0.11685150861740112, 0.13423563539981842, 0.137895867228508, 0.07430413365364075, 0.11526723951101303, 0.05180691182613373, 0.041291914880275726, 0.10831441730260849, 0.06834227591753006, 0.015879690647125244, 0.1678687185049057, 0.047342896461486816, 0.12794160842895508, 0.10289439558982849, 0.10082995891571045, 0.14155711233615875, 0.0842529684305191, 0.16915874183177948, 0.1010451465845108, 0.13642559945583344, 0.08876153826713562, 0.13519752025604248, 0.18436813354492188, 0.131959468126297, 0.14466778934001923, 0.04653974249958992, 0.11932998150587082, 0.04196137189865112, 0.08924835920333862, 0.08537767082452774, 0.1184384673833847, 0.1615256816148758, 0.116963692009449, 0.0664077177643776, 0.08104799687862396, 0.08205125480890274, 0.11173616349697113, 0.18147988617420197, 0.13987737894058228, 0.04648040607571602, 0.040101706981658936, 0.07807350903749466, 0.039986252784729004, 0.1327146291732788, 0.17230813205242157, 0.11162790656089783, 0.16423936188220978, 0.12927357852458954, 0.12293285131454468, 0.09905809164047241, 0.1473696529865265, 0.1771204024553299, 0.18340682983398438, 0.19286587834358215, 0.08863364905118942, 0.2001819610595703, 0.06139156222343445, 0.05256259813904762, 0.1188383623957634, 0.11129005253314972, 0.1169619932770729, 0.10187486559152603, 0.1275848001241684, 0.08973249047994614, 0.1026720404624939, 0.09461192041635513, 0.08354616165161133, 0.10089118778705597, 0.06120193377137184, 0.08732946217060089, 0.15587812662124634, 0.12450996041297913, 0.16077381372451782, 0.07868489623069763, 0.152043879032135, 0.11609554290771484, 0.12362793833017349, 0.09371234476566315, 0.16221897304058075, 0.07209722697734833, 0.09105753898620605, 0.17856600880622864, 0.0953841283917427, 0.15400701761245728, 0.044457606971263885, 0.057490024715662, 0.15740159153938293, 0.11111537367105484, 0.08859598636627197, 0.11739261448383331, 0.0419745147228241, 0.10894433408975601, 0.053444456309080124, 0.13617539405822754, 0.13450419902801514, 0.10833152383565903, 0.18825885653495789, 0.12562993168830872, 0.05928999185562134, 0.08982516825199127, 0.22975844144821167, 0.09136952459812164, 0.13920356333255768, 0.12025611847639084, 0.1566530019044876, 0.11402356624603271, 0.11683493107557297, 0.17822323739528656, 0.14753133058547974, 0.11823610216379166, 0.14962132275104523, 0.11002945899963379, 0.12933829426765442, 0.10809463262557983, 0.13527292013168335, 0.09275709092617035, 0.09840132296085358, 0.0754493698477745, 0.09393632411956787, 0.1535598784685135, 0.18000049889087677, 0.15118886530399323, 0.13442903757095337, 0.17058348655700684, 0.10407823324203491, 0.12811584770679474, 0.08052510768175125, 0.12298471480607986, 0.07689284533262253, 0.1576627492904663, 0.05843978747725487, 0.10830971598625183, 0.1102088913321495, 0.1460287868976593, 0.0519225187599659, 0.11145433038473129, 0.1384889781475067, 0.07658454030752182, 0.06531800329685211, 0.08832073211669922, 0.08781719207763672, 0.08431869000196457, 0.11764813959598541, 0.09744352102279663, 0.11346954852342606, 0.09088251739740372, 0.14498090744018555, 0.12467033416032791, 0.14954350888729095, 0.0826406478881836, 0.1349976509809494, 0.10116775333881378, 0.08669155091047287, 0.13839706778526306, 0.09337782859802246, 0.09308568388223648, 0.12215274572372437, 0.08761906623840332, 0.10217268764972687, 0.1061851978302002, 0.1713937222957611, 0.11444062739610672, 0.15152692794799805, 0.14024609327316284, 0.10963591933250427, 0.07550259679555893, 0.12021113932132721, 0.07464706897735596, 0.12329238653182983, 0.06304968893527985, 0.08010156452655792, 0.11489740014076233, 0.14212284982204437, 0.14222006499767303, 0.14761757850646973, 0.10215725004673004, 0.09132420271635056, 0.12052774429321289, 0.12077464163303375, 0.12267811596393585, 0.12134873867034912, 0.08865558356046677, 0.07091382145881653, 0.10892583429813385, 0.056700944900512695, 0.1461295634508133, 0.12882038950920105, 0.0933491587638855, 0.13846591114997864, 0.1443391889333725, 0.09678071737289429, 0.16074642539024353, 0.11365966498851776, 0.10058511793613434, 0.05970141291618347, 0.1438770592212677, 0.07256335020065308, 0.13505955040454865, 0.11185097694396973, 0.11255599558353424, 0.07218316197395325, 0.14635109901428223, 0.13607154786586761, 0.1050637811422348, 0.110680490732193, 0.12639594078063965, 0.11744380742311478, 0.14465224742889404, 0.1427452564239502, 0.0812598392367363, 0.12846527993679047, 0.09622764587402344, 0.1941690444946289, 0.1592627614736557, 0.16192886233329773, 0.09391079097986221, 0.23029878735542297, 0.14919717609882355, 0.0996464341878891, 0.13691382110118866, 0.12302988022565842, 0.06634938716888428, 0.08043640851974487, 0.10204237699508667, 0.10904095321893692, 0.13373497128486633, 0.05549895763397217, 0.04128897935152054, 0.1266903579235077, 0.14843499660491943, 0.16018247604370117, 0.13378651440143585, 0.017154820263385773, 0.15321867167949677, 0.04746430739760399, 0.06108100712299347, 0.10034078359603882, 0.1050417423248291, 0.05695899948477745, 0.12687565386295319, 0.13398510217666626, 0.16531924903392792, 0.11340566724538803, 0.14142273366451263, 0.11526184529066086, 0.15617381036281586, 0.14818289875984192, 0.06860216706991196, 0.18740732967853546, 0.10210661590099335, 0.08062322437763214, 0.14516912400722504, 0.18461883068084717, 0.11780496686697006, 0.18079198896884918, 0.07166048139333725, 0.17438946664333344, 0.1882791519165039, 0.16823318600654602, 0.1587563306093216, 0.06737759709358215, 0.144645094871521, 0.18019889295101166, 0.12647822499275208, 0.08915036916732788, 0.17894557118415833, 0.09850287437438965, 0.1313791573047638, 0.12118297070264816, 0.10417522490024567, 0.1248738169670105, 0.09263189136981964, 0.031322553753852844, 0.11053284257650375, 0.05166548490524292, 0.15489403903484344, 0.14645878970623016, 0.10789657384157181, 0.46296262741088867, 0.5027100443840027, 1.1642272472381592, 0.6421023607254028, 0.8167860507965088, 0.48108774423599243, 0.9959755539894104, 0.604290783405304, 0.8773843050003052, 0.5943970084190369, 0.5738738775253296, 0.696944534778595, 0.9384090900421143, 0.7720587849617004, 0.4805806279182434, 0.9377438426017761, 0.6387900114059448, 0.43011876940727234, 0.7830320596694946, 1.1327099800109863, 0.6664630174636841, 0.8975175023078918, 0.6631284952163696, 0.5215362906455994, 0.7718745470046997, 1.358652949333191, 0.6758047342300415, 0.5837297439575195, 0.605687141418457, 0.8436440825462341, 0.8915642499923706, 0.5559669137001038, 1.1762678623199463, 0.9962865710258484, 0.9436743855476379, 0.9710688591003418, 0.9356535077095032, 1.1535273790359497, 0.6958320736885071, 0.6089955568313599, 1.006318211555481, 0.950437068939209, 0.5879475474357605, 0.6197689771652222, 0.5127676129341125, 0.7166478037834167, 0.56853848695755, 0.8336844444274902, 1.1841204166412354, 1.1370768547058105, 0.936664879322052, 0.7983862161636353, 0.787735104560852, 0.7558383941650391, 0.6912412643432617, 0.8697760701179504, 1.0733959674835205, 0.6310005187988281, 0.5072606205940247, 0.8297218680381775, 0.45198073983192444, 0.6572102308273315, 0.4831385016441345, 0.5714707970619202, 1.0346615314483643, 0.6405280232429504, 0.6240594983100891, 0.44920626282691956, 0.845024824142456, 0.6381930112838745, 1.3474328517913818, 0.4787937104701996, 0.8478334546089172, 0.9349706768989563, 0.43677818775177, 0.9757992625236511, 0.5873506665229797, 0.9503657221794128, 0.6066834926605225, 0.5070153474807739, 0.7767167687416077, 0.7713673710823059, 0.5044286847114563, 0.4811723232269287, 0.5939635038375854, 0.29634737968444824, 0.6757745146751404, 0.6331615447998047, 0.5177165269851685, 0.5689558982849121, 0.6864255666732788, 0.7183735370635986, 1.19243323802948, 0.2323724627494812, 1.0029304027557373, 0.6963578462600708, 0.7187415957450867, 0.6385807394981384, 0.7650944590568542, 0.4521080553531647, 1.427633285522461, 0.6681512594223022, 0.6323740482330322, 0.8028703927993774, 0.697091281414032, 0.6095311641693115, 1.1495156288146973, 0.4574391841888428, 0.7349219918251038, 0.6005514860153198, 0.4466331899166107, 0.5297806262969971, 1.1042742729187012, 0.6981422305107117, 0.7908530235290527, 0.5209383964538574, 0.8394158482551575, 1.1646592617034912, 0.5582438707351685, 0.615803599357605, 0.5279567241668701, 0.47796788811683655, 0.6398177146911621, 0.43727928400039673, 0.5364277362823486, 0.7037544250488281, 0.6769082546234131, 0.5507669448852539, 1.042544960975647, 0.6244697570800781, 1.0407590866088867, 0.7533171772956848, 1.0976123809814453, 0.3577083647251129, 0.9015515446662903, 0.8393210172653198, 0.7114884257316589, 0.8073240518569946, 0.39047929644584656, 1.3153350353240967, 0.9103466868400574, 0.524606466293335, 0.6675708889961243, 0.6026773452758789, 0.6682140827178955, 0.7144673466682434, 0.9047813415527344, 0.8221389651298523, 0.42548391222953796, 1.1588166952133179, 0.788978099822998, 0.8633812665939331, 0.8165223002433777, 0.6874237060546875, 0.6397870779037476, 0.8855525255203247, 0.5684077739715576, 0.7666096091270447, 0.981198251247406, 0.8622059226036072, 0.5799057483673096, 1.3633654117584229, 0.6906666159629822, 0.7038002610206604, 0.36134830117225647, 1.1986870765686035, 0.7150333523750305, 0.5517750978469849, 0.3903471529483795, 0.6489827036857605, 0.32041820883750916, 1.1311168670654297, 1.0106720924377441, 0.8062731623649597, 0.8533415794372559, 0.9299132823944092, 0.7364048361778259, 0.7220787405967712, 1.1723682880401611, 0.6348851919174194, 0.5766420364379883, 1.137284517288208, 0.6832162141799927, 0.4751066565513611, 0.5501198768615723, 0.5298082828521729, 0.9511664509773254, 0.620158851146698, 0.9457184672355652, 0.7391090393066406, 0.45877161622047424, 0.5036097764968872, 0.8697758913040161, 0.6875209808349609, 0.9401730298995972, 0.5714155435562134, 0.48580893874168396, 1.1142776012420654, 0.7026138305664062, 1.3933993577957153, 0.41821691393852234, 1.2196978330612183, 0.9470517039299011, 0.7587316632270813, 0.4390077590942383, 0.7035128474235535, 1.1188932657241821, 0.5613371729850769, 0.8314327597618103, 0.7282174229621887, 0.9227955341339111, 0.9383668303489685, 0.4796110689640045, 1.2104649543762207, 1.5806702375411987, 0.695380687713623, 0.9406608939170837, 0.7947573661804199, 0.525917649269104, 0.6102240085601807, 0.5072019696235657, 0.5189689993858337, 1.0206125974655151, 0.4517250657081604, 0.9031669497489929, 0.5573663711547852, 0.6433043479919434, 0.9346728324890137, 0.5255409479141235, 1.0176877975463867, 0.8828107118606567, 0.8119150996208191, 1.0431780815124512, 1.0305285453796387, 0.48225146532058716, 0.7257007956504822, 0.8180825114250183, 0.9471859335899353, 1.147383213043213, 0.8579431772232056, 0.7621945142745972, 1.0847625732421875, 0.7350611686706543, 0.7073726654052734, 0.4287814199924469, 0.859856367111206, 0.8974902033805847, 0.46754270792007446, 1.2856619358062744, 1.0712206363677979, 0.8975500464439392, 0.49498358368873596, 0.7569268345832825, 0.9961497783660889, 0.4563220143318176, 0.6730274558067322, 0.9277758598327637, 0.6482961773872375, 0.8870686292648315, 0.4391704499721527, 0.7596699595451355, 0.7231688499450684, 0.6163433194160461, 0.4791582524776459, 0.7978851199150085, 0.45837488770484924, 0.7657705545425415, 1.4656671285629272, 0.9110396504402161, 0.6143031716346741, 0.8006453514099121, 0.6713494658470154, 0.5872892141342163, 0.641901969909668, 0.9160799980163574, 0.8672069907188416, 1.1340445280075073, 0.7799432277679443, 0.6805033683776855, 0.9712574481964111, 1.018488883972168, 0.40274444222450256, 0.9793426394462585, 0.41326603293418884, 1.2202966213226318, 1.238931655883789, 0.9060337543487549, 0.8983456492424011, 0.350839227437973, 1.1318118572235107, 0.7428995370864868, 1.0001325607299805, 1.3906713724136353, 0.33447566628456116, 1.2716785669326782, 0.47052866220474243, 0.9786897897720337, 1.4998421669006348, 0.613921046257019, 0.6268558502197266, 92.02349090576172, 69.46585083007812, 113.43486785888672, 40.87860107421875, 36.375823974609375, 75.710205078125, 14.0543212890625, 38.20852279663086, 44.46503829956055, 14.157756805419922, 14.945710182189941, 84.4239273071289, 31.237022399902344, 86.481201171875, 140.95831298828125, 38.745670318603516, 20.434499740600586, 21.58405876159668, 66.9432373046875, 16.00067138671875, 52.77490997314453, 64.85983276367188, 42.89992904663086, 91.037353515625, 92.17173767089844, 56.18227767944336, 92.68960571289062, 38.61317443847656, 128.04034423828125, 37.605194091796875, 79.06509399414062, 48.66688537597656, 37.55888366699219, 53.223602294921875, 41.840576171875, 51.73080825805664, 43.20083236694336, 19.450927734375, 44.69851303100586, 32.48968505859375, 38.71240234375, 53.40472412109375, 88.3375015258789, 98.74419403076172, 22.552963256835938, 88.82307434082031, 39.02301788330078, 117.21209716796875, 55.127479553222656, 33.284751892089844, 104.84624481201172, 71.81689453125, 36.29827880859375, 32.27717208862305, 133.64425659179688, 25.819686889648438, 22.594207763671875, 26.57647705078125, 30.126230239868164, 49.641170501708984, 63.9963493347168, 15.997979164123535, 47.0545654296875, 44.31028747558594, 14.067296981811523, 62.734375, 24.93425750732422, 15.006364822387695, 64.87423706054688, 54.541351318359375, 59.33929443359375, 31.67790985107422, 19.020263671875, 40.23748779296875, 28.247333526611328, 11.309661865234375, 26.456457138061523, 17.54193115234375, 16.349044799804688, 31.28851318359375, 128.45518493652344, 26.6357421875, 96.34843444824219, 67.28536987304688, 88.072509765625, 16.804656982421875, 54.41801452636719, 90.6097640991211, 36.79388427734375, 40.136634826660156, 59.0987548828125, 14.993644714355469, 77.61585998535156, 46.59886169433594, 80.56851959228516, 58.230525970458984, 17.3824462890625, 18.82831573486328, 10.895294189453125, 104.47982025146484, 25.02455711364746, 30.950040817260742, 40.836273193359375, 78.30668640136719, 25.799222946166992, 81.78378295898438, 36.152923583984375, 18.895843505859375, 92.281494140625, 39.2060432434082, 64.992919921875, 18.888031005859375, 18.579484939575195, 10.020599365234375, 64.01444244384766, 16.59083366394043, 15.11431884765625, 13.24489974975586, 67.35751342773438, 15.5628662109375, 89.66455078125, 49.41781997680664, 40.28925323486328, 44.91250228881836, 35.59959411621094, 15.563556671142578, 124.77163696289062, 36.14260482788086, 118.30410766601562, 57.591552734375, 89.44591522216797, 42.077938079833984, 18.01948356628418, 166.30429077148438, 26.91363525390625, 79.70030212402344, 28.0953369140625, 57.12042999267578, 22.866546630859375, 64.4954833984375, 23.807464599609375, 52.848236083984375, 141.79345703125, 18.933916091918945, 70.88408660888672, 66.40664672851562, 22.36761474609375, 69.2709732055664, 15.87286376953125, 25.90167236328125, 33.7449951171875, 23.842742919921875, 63.00825119018555, 14.349196434020996, 100.77591705322266, 59.31155776977539, 121.031005859375, 22.094451904296875, 37.55078887939453, 29.18572998046875, 16.65681266784668, 25.677152633666992, 71.68107604980469, 44.39329147338867, 59.28605270385742, 16.786396026611328, 62.7676887512207, 26.41668701171875, 146.02352905273438, 15.599184036254883, 58.61405944824219, 81.84732055664062, 54.440589904785156, 87.70333099365234, 20.974271774291992, 103.15435028076172, 14.997997283935547, 37.71591567993164, 60.60725402832031, 32.45487976074219, 57.13714599609375, 60.232879638671875, 43.56352615356445, 16.73666000366211, 22.36347198486328, 16.5362548828125, 16.110177993774414, 33.409549713134766, 56.78748321533203, 36.349090576171875, 25.17768669128418, 33.750492095947266, 29.028533935546875, 58.98936462402344, 36.991455078125, 126.54705047607422, 28.63612174987793, 36.165283203125, 139.74598693847656, 21.1351318359375, 22.21280288696289, 65.99454498291016, 18.36386489868164, 40.81751251220703, 55.56488037109375, 54.7276611328125, 12.991568565368652, 52.27864074707031, 35.46400451660156, 19.324203491210938, 55.32977294921875, 76.64241027832031, 44.947792053222656, 67.80070495605469, 14.508453369140625, 162.91796875, 60.290042877197266, 15.077248573303223, 71.27593231201172, 133.47683715820312, 58.86368179321289, 59.20281982421875, 19.43035888671875, 14.823122024536133, 38.14032745361328, 51.86534881591797, 59.969295501708984, 30.800004959106445, 23.515581130981445, 289.2561340332031, 43.96761703491211, 82.378662109375, 38.27192687988281, 18.274599075317383, 30.450653076171875, 82.2206039428711, 122.9023208618164, 66.16509246826172, 71.27084350585938, 87.52505493164062, 18.830835342407227, 38.36355209350586, 13.181258201599121, 14.33135986328125, 76.90142059326172, 49.31732177734375, 25.57972526550293, 74.71183776855469, 128.69483947753906, 54.68174743652344, 21.842147827148438, 139.08648681640625, 49.937744140625, 47.7437744140625, 73.54653930664062, 17.08873176574707, 21.497411727905273, 71.92206573486328, 16.662506103515625, 13.363082885742188, 110.66525268554688, 63.7336311340332, 127.604736328125, 53.4617919921875, 37.660125732421875, 24.964139938354492, 82.867919921875, 51.097412109375, 33.555870056152344, 17.051267623901367, 112.0018539428711, 23.7281494140625, 42.753753662109375, 61.38332748413086, 135.39187622070312, 51.422943115234375, 16.811372756958008, 69.72119140625, 35.73516845703125, 93.0540771484375, 23.97504997253418, 77.52249145507812, 24.67283821105957, 67.38455963134766, 70.3607177734375, 52.49815368652344, 54.93742370605469, 47.395477294921875, 64.58601379394531, 48.26393508911133, 43.89589309692383, 60.86880111694336, 174.7351531982422, 38.303245544433594, 22.824604034423828, 28.93735694885254, 38.80265808105469, 39.01492691040039, 34.833709716796875, 60.922607421875, 1.9460999965667725, 1.9728225469589233, 1.6515411138534546, 1.837563395500183, 2.1611459255218506, 2.6395068168640137, 1.7243337631225586, 1.6724385023117065, 2.927971839904785, 3.1963837146759033, 2.3000845909118652, 1.174025535583496, 2.2637739181518555, 1.4790539741516113, 2.460939645767212, 2.5144760608673096, 2.252143621444702, 3.5869131088256836, 2.0242013931274414, 2.4562485218048096, 1.6933640241622925, 2.182629346847534, 2.05399751663208, 3.2683122158050537, 2.9815587997436523, 1.712766408920288, 1.6984604597091675, 1.6147249937057495, 2.330203056335449, 2.1331186294555664, 2.804764986038208, 2.589569568634033, 2.203247308731079, 1.8776344060897827, 1.7183599472045898, 3.0296261310577393, 2.941729784011841, 3.2956154346466064, 1.8566597700119019, 3.1368072032928467, 1.5449365377426147, 2.3797125816345215, 1.9054737091064453, 2.109844923019409, 1.564223289489746, 1.4897642135620117, 2.7077081203460693, 2.1121468544006348, 2.5425539016723633, 1.758492350578308, 2.3723275661468506, 2.1028738021850586, 2.100943088531494, 2.6145224571228027, 2.311429023742676, 2.1976919174194336, 1.8434972763061523, 1.7586623430252075, 3.495267868041992, 2.1760358810424805, 2.4435815811157227, 2.90269136428833, 1.843555212020874, 1.6990957260131836, 2.408606767654419, 1.4932068586349487, 1.7479188442230225, 1.8750332593917847, 1.734419822692871, 1.8771719932556152, 2.6503257751464844, 2.35595703125, 1.9748543500900269, 1.6689176559448242, 1.182551383972168, 1.713228464126587, 1.7732419967651367, 1.4888828992843628, 2.31313419342041, 2.829798460006714, 1.634185791015625, 2.5268166065216064, 1.9272289276123047, 2.54638671875, 3.1043827533721924, 1.476921796798706, 2.510127067565918, 2.2324905395507812, 2.695544481277466, 1.9777026176452637, 1.75095534324646, 2.3939082622528076, 3.0194478034973145, 3.176278591156006, 2.072333574295044, 2.7211360931396484, 1.6028900146484375, 2.612081527709961, 2.006558418273926, 2.9945178031921387, 2.526188373565674, 2.397444725036621, 2.6844122409820557, 1.057586669921875, 1.3857080936431885, 1.7682238817214966, 1.3908113241195679, 2.3137292861938477, 3.082169771194458, 1.6773340702056885, 2.7806406021118164, 1.2367075681686401, 1.8512296676635742, 2.8885116577148438, 2.5263092517852783, 1.6219531297683716, 2.48964786529541, 2.711186408996582, 2.1078946590423584, 2.9292547702789307, 2.4977312088012695, 3.130375862121582, 1.874516248703003, 1.7062618732452393, 1.6523791551589966, 1.681563377380371, 1.689199686050415, 0.9179426431655884, 1.4664602279663086, 2.0068235397338867, 1.2150589227676392, 1.9523688554763794, 1.7695895433425903, 2.8089654445648193, 1.9990942478179932, 1.92512845993042, 2.0855722427368164, 1.792227864265442, 2.287882089614868, 1.8414429426193237, 1.7785911560058594, 2.819018602371216, 1.9331485033035278, 2.3848631381988525, 2.311816692352295, 1.873940348625183, 2.299652576446533, 2.2741808891296387, 2.4346652030944824, 2.100602865219116, 2.146056890487671, 1.4079846143722534, 1.8382967710494995, 1.9969452619552612, 2.9019341468811035, 1.8769234418869019, 2.8053526878356934, 3.0411272048950195, 1.6122546195983887, 2.5241289138793945, 3.2693169116973877, 2.173750877380371, 1.7275843620300293, 2.801882266998291, 2.421307325363159, 1.9830814599990845, 2.1309421062469482, 3.225794792175293, 2.4882709980010986, 2.8048675060272217, 1.1906899213790894, 2.1920299530029297, 3.2117068767547607, 1.8473788499832153, 1.9744271039962769, 2.8132359981536865, 2.4533281326293945, 2.5535383224487305, 2.2875990867614746, 1.8651151657104492, 1.5288444757461548, 2.7650580406188965, 1.7693835496902466, 2.2924718856811523, 2.960700273513794, 2.4834845066070557, 2.0515050888061523, 2.3295602798461914, 2.261859178543091, 2.123293876647949, 1.7911072969436646, 1.7663177251815796, 2.920494556427002, 2.890035629272461, 2.1228461265563965, 2.6507959365844727, 2.7752978801727295, 3.3323686122894287, 2.9156177043914795, 2.672865629196167, 1.6609678268432617, 2.0584802627563477, 2.3120079040527344, 1.8103913068771362, 1.7613270282745361, 2.1520321369171143, 1.3669934272766113, 1.541029930114746, 2.2270891666412354, 1.339430809020996, 1.8657344579696655, 2.326169013977051, 1.974909782409668, 1.5933510065078735, 1.9258511066436768, 2.191094398498535, 1.4687986373901367, 2.7694385051727295, 2.08126163482666, 2.1643195152282715, 1.8435066938400269, 2.8445231914520264, 1.4997063875198364, 2.0430092811584473, 2.486299991607666, 2.4069197177886963, 1.4184322357177734, 1.8262438774108887, 2.612227201461792, 2.912686586380005, 3.287355899810791, 1.706823706626892, 2.543365955352783, 1.1166410446166992, 1.444924235343933, 1.2999924421310425, 2.1826956272125244, 1.5091296434402466, 2.3949105739593506, 2.364609718322754, 2.502621650695801, 2.2519619464874268, 1.944693922996521, 2.3470592498779297, 3.0249481201171875, 2.877150535583496, 2.0293755531311035, 2.5168182849884033, 1.769209861755371, 1.3898649215698242, 2.3860561847686768, 1.9841833114624023, 3.59447979927063, 2.6750519275665283, 2.1850054264068604, 2.1340224742889404, 1.6270437240600586, 1.837881088256836, 2.0630741119384766, 2.110063076019287, 1.9229934215545654, 2.280494213104248, 2.044360876083374, 1.9195140600204468, 2.5510077476501465, 0.9572515487670898, 1.8401039838790894, 2.4368770122528076, 2.072772979736328, 1.6002962589263916, 2.733333110809326, 2.3777990341186523, 1.8618539571762085, 1.7202919721603394, 1.421059489250183, 2.117617607116699, 2.115922212600708, 2.0229501724243164, 1.691054344177246, 1.7016935348510742, 2.682161808013916, 2.4512338638305664, 2.054908037185669, 3.0943386554718018, 2.590691566467285, 3.179612398147583, 1.9073930978775024, 2.538569688796997, 1.547163963317871, 1.8177006244659424, 2.6777184009552, 3.127497911453247, 1.5587399005889893, 2.7010605335235596, 2.609051465988159, 2.7279586791992188, 2.783212423324585, 3.282076835632324, 2.212813377380371, 3.4054534435272217, 0.10126309841871262, 0.10314257442951202, 0.042448222637176514, 0.14445269107818604, 0.14006848633289337, 0.09321656078100204, 0.14866065979003906, 0.13513293862342834, 0.16974052786827087, 0.11423154920339584, 0.12196164578199387, 0.1398134082555771, 0.17165547609329224, 0.10278046131134033, 0.12291944026947021, 0.0748589038848877, 0.16839070618152618, 0.1089225709438324, 0.12522685527801514, 0.10315578430891037, 0.06999146193265915, 0.10426831245422363, 0.10381579399108887, 0.08967550098896027, 0.10721637308597565, 0.22824521362781525, 0.11845260113477707, 0.116858571767807, 0.06572132557630539, 0.09514390677213669, 0.11617495864629745, 0.13233564794063568, 0.10373520851135254, 0.10358992218971252, 0.10070354491472244, 0.12339939922094345, 0.12353780120611191, 0.11037565767765045, 0.15611088275909424, 0.10341490805149078, 0.13944268226623535, 0.07249117642641068, 0.18255798518657684, 0.172219917178154, 0.09077884256839752, 0.12032536417245865, 0.1612282544374466, 0.15516923367977142, 0.06314809620380402, 0.10253885388374329, 0.07104946672916412, 0.05318067595362663, 0.0980343446135521, 0.045160796493291855, 0.15281081199645996, 0.13689111173152924, 0.10075508058071136, 0.07436303794384003, 0.07913020253181458, 0.1461823582649231, 0.07620804011821747, 0.09748023748397827, 0.1604287475347519, 0.17599248886108398, 0.07125253975391388, 0.12742964923381805, 0.17647992074489594, 0.08313868939876556, 0.17067094147205353, 0.10698091238737106, 0.14168089628219604, 0.10522879660129547, 0.11077148467302322, 0.07620552182197571, 0.10206584632396698, 0.08747509121894836, 0.13041546940803528, 0.13335976004600525, 0.1263655573129654, 0.13368605077266693, 0.07314903289079666, 0.08103466033935547, 0.09909980744123459, 0.1700839251279831, 0.13864517211914062, 0.08075080811977386, 0.18855105340480804, 0.08197549730539322, 0.12587827444076538, 0.13443098962306976, 0.02417910099029541, 0.13275517523288727, 0.16666004061698914, 0.10542762279510498, 0.11893699318170547, 0.07995212078094482, 0.13408096134662628, 0.14278960227966309, 0.07580430060625076, 0.11306437849998474, 0.1573714017868042, 0.08683495968580246, 0.13864870369434357, 0.0629911720752716, 0.09589526802301407, 0.1445271223783493, 0.12893712520599365, 0.1343030333518982, 0.10211852937936783, 0.10033325105905533, 0.09996166080236435, 0.1049526110291481, 0.10270527750253677, 0.06271307170391083, 0.04913406819105148, 0.17513637244701385, 0.05906529352068901, 0.1477857381105423, 0.12199749052524567, 0.15772250294685364, 0.09270542860031128, 0.18587806820869446, 0.09316062927246094, 0.09867220371961594, 0.10577346384525299, 0.16733308136463165, 0.15032458305358887, 0.10103721171617508, 0.1283944994211197, 0.10650282353162766, 0.11292237788438797, 0.03654517978429794, 0.15689705312252045, 0.14080356061458588, 0.0694265142083168, 0.1960640698671341, 0.07249479740858078, 0.10838242620229721, 0.12850040197372437, 0.10840562731027603, 0.11982158571481705, 0.11072426289319992, 0.14910587668418884, 0.18758223950862885, 0.113082654774189, 0.07802895456552505, 0.09738409519195557, 0.0270752664655447, 0.14974552392959595, 0.08693911135196686, 0.14042340219020844, 0.1010320633649826, 0.10803306102752686, 0.17877589166164398, 0.10727944225072861, 0.14696845412254333, 0.15932685136795044, 0.12388581037521362, 0.10915865749120712, 0.07884833961725235, 0.12067965418100357, 0.14628010988235474, 0.08521544933319092, 0.08355533331632614, 0.13385404646396637, 0.176951602101326, 0.1999109983444214, 0.11999090015888214, 0.08343879878520966, 0.12911391258239746, 0.0937962532043457, 0.11511886119842529, 0.08860557526350021, 0.1546146422624588, 0.08583445101976395, 0.0781303122639656, 0.1649208813905716, 0.10292495787143707, 0.08892558515071869, 0.13696342706680298, 0.0193836260586977, 0.06001162528991699, 0.08841054886579514, 0.11112485826015472, 0.13047772645950317, 0.11004775017499924, 0.06026184558868408, 0.13161014020442963, 0.17791138589382172, 0.07670532166957855, 0.08849028497934341, 0.0845574364066124, 0.1150299459695816, 0.10999640822410583, 0.15302997827529907, 0.14620378613471985, 0.10313880443572998, 0.09517152607440948, 0.14136174321174622, 0.1711728274822235, 0.13220858573913574, 0.13733278214931488, 0.1601230800151825, 0.1724669635295868, 0.15428805351257324, 0.11338850110769272, 0.13858914375305176, 0.05777690187096596, 0.12987948954105377, 0.07536095380783081, 0.09126442670822144, 0.13440270721912384, 0.1564212441444397, 0.06711647659540176, 0.1689450740814209, 0.13768549263477325, 0.09629183262586594, 0.08806341886520386, 0.09321517497301102, 0.062383055686950684, 0.032429516315460205, 0.12575966119766235, 0.05692581087350845, 0.14466895163059235, 0.06649770587682724, 0.13581424951553345, 0.11411937326192856, 0.07223909348249435, 0.1294080913066864, 0.06884574145078659, 0.14147406816482544, 0.09370273351669312, 0.17387504875659943, 0.09979522228240967, 0.10955911129713058, 0.11185628920793533, 0.06944193691015244, 0.10516883432865143, 0.14596015214920044, 0.11689534038305283, 0.08762234449386597, 0.08004533499479294, 0.09846313297748566, 0.15946173667907715, 0.11554956436157227, 0.16260218620300293, 0.05606621131300926, 0.1047183945775032, 0.1142207607626915, 0.1072738841176033, 0.09929913282394409, 0.0835539698600769, 0.10348037630319595, 0.08373105525970459, 0.08333171904087067, 0.11678513884544373, 0.14776812493801117, 0.07966309040784836, 0.06892137229442596, 0.06816837936639786, 0.10985596477985382, 0.14358408749103546, 0.16404154896736145, 0.1686774343252182, 0.060104262083768845, 0.17016682028770447, 0.14152789115905762, 0.09451467543840408, 0.18392013013362885, 0.0878048986196518, 0.10276863723993301, 0.0600554458796978, 0.10273301601409912, 0.1278640627861023, 0.1134822890162468, 0.07148698717355728, 0.06221574544906616, 0.19182540476322174, 0.13435795903205872, 0.1567571759223938, 0.14472350478172302, 0.1001570075750351, 0.15766216814517975, 0.10737674683332443, 0.14911764860153198, 0.1125212237238884, 0.15987439453601837, 0.10841298848390579, 0.044178880751132965, 0.09138168394565582, 0.11433687061071396, 0.14852750301361084, 0.19888734817504883, 0.12921760976314545, 0.14299531280994415, 0.07092162221670151, 0.1158122792840004, 0.1411924511194229, 0.10038410127162933, 0.12002884596586227, 0.9477499127388, 0.8558680415153503, 1.0746848583221436, 0.7548438906669617, 1.2702970504760742, 0.8105496168136597, 0.7120863199234009, 1.1530077457427979, 0.7207555770874023, 0.5597842335700989, 0.9372074007987976, 1.1419308185577393, 0.8813417553901672, 1.2151306867599487, 0.5752978920936584, 0.9123364090919495, 0.3486248552799225, 0.5326204299926758, 0.9783145189285278, 0.8994903564453125, 0.6777313947677612, 0.7177155613899231, 1.1601003408432007, 1.1521494388580322, 0.7545321583747864, 0.44770893454551697, 0.9146850109100342, 0.6481596231460571, 1.0358569622039795, 0.7775607109069824, 0.8306416273117065, 0.6028664112091064, 0.7318857312202454, 0.7668665051460266, 1.0598310232162476, 0.4778729975223541, 0.6643595099449158, 0.9963358044624329, 0.7293241620063782, 0.529288649559021, 0.7973648905754089, 0.9398423433303833, 0.7343568205833435, 0.758073091506958, 0.8888574838638306, 0.642720639705658, 0.7249887585639954, 0.989145815372467, 1.301755666732788, 0.952707827091217, 0.6824584603309631, 0.9782876372337341, 0.5076229572296143, 0.5758775472640991, 1.191470742225647, 0.48891741037368774, 0.8785069584846497, 0.8917739391326904, 0.7317484021186829, 0.7262916564941406, 1.0614001750946045, 1.1972042322158813, 0.7691505551338196, 1.2107576131820679, 0.7193272709846497, 0.9850088357925415, 0.7248144149780273, 0.7347868084907532, 1.1136112213134766, 0.6923978924751282, 0.7091784477233887, 0.7120379209518433, 0.5285828113555908, 0.4344417154788971, 1.005792498588562, 1.114277720451355, 1.2290894985198975, 0.6471542119979858, 0.8253728151321411, 0.5700187683105469, 0.5621979236602783, 1.2581570148468018, 0.9078238606452942, 0.5463211536407471, 1.5628830194473267, 0.8204072117805481, 1.0804263353347778, 0.7779520153999329, 0.4654861390590668, 0.5257260799407959, 0.4884158670902252, 0.4760713577270508, 0.6900850534439087, 0.8307458162307739, 0.7717437744140625, 0.9544464945793152, 0.7208473086357117, 0.4365215301513672, 0.9016079306602478, 1.1982072591781616, 0.5870293378829956, 0.9143974184989929, 1.133492350578308, 0.7787163853645325, 0.5650916695594788, 0.6286163330078125, 0.6649125814437866, 1.0204459428787231, 1.1081583499908447, 1.0006756782531738, 0.5881767868995667, 0.701684296131134, 0.4059717357158661, 0.7751733064651489, 1.31822669506073, 0.9318564534187317, 1.217378854751587, 0.49524885416030884, 0.9264930486679077, 0.665217399597168, 0.8549679517745972, 0.8316033482551575, 0.8694300651550293, 1.5089584589004517, 0.8117738366127014, 0.35367971658706665, 0.6789960861206055, 1.0388102531433105, 0.8011995553970337, 0.6847662925720215, 0.9907211661338806, 0.3877672553062439, 1.2430191040039062, 1.12811279296875, 0.7669293284416199, 0.6912286281585693, 0.8325121998786926, 1.0030115842819214, 0.7145436406135559, 0.7851328253746033, 0.7421091198921204, 0.788131058216095, 1.0486185550689697, 0.742598831653595, 0.6872313618659973, 1.1141657829284668, 0.7585340738296509, 0.4479329586029053, 0.46536561846733093, 0.8172657489776611, 1.1756798028945923, 0.5742695331573486, 1.0753581523895264, 0.2547696828842163, 0.8370664715766907, 1.1585749387741089, 0.8567086458206177, 1.2994674444198608, 0.6053591966629028, 0.9606610536575317, 1.0804184675216675, 0.6952067613601685, 0.458240270614624, 0.7140843272209167, 0.7690923810005188, 0.6404498219490051, 0.7579606175422668, 0.9130939841270447, 0.41222989559173584, 1.13023841381073, 0.7318585515022278, 1.03150475025177, 0.868230938911438, 0.5843572020530701, 0.9265346527099609, 0.7962619662284851, 0.5171977281570435, 0.7987570762634277, 0.7788119316101074, 0.5481530427932739, 0.4305797517299652, 0.7185986638069153, 0.9743094444274902, 1.0257911682128906, 0.4180908203125, 0.9887102246284485, 1.3492405414581299, 0.8411094546318054, 0.29901155829429626, 0.7544655203819275, 0.5856821537017822, 0.8082571029663086, 1.126538872718811, 0.8399247527122498, 1.0567011833190918, 1.0114132165908813, 0.847501277923584, 1.1409544944763184, 0.6278271079063416, 0.8121450543403625, 0.40855926275253296, 0.7193569540977478, 0.6135161519050598, 1.2614127397537231, 0.7795345783233643, 0.9995748400688171, 0.9710586071014404, 0.5626176595687866, 0.9922782778739929, 0.545985996723175, 0.9369475841522217, 0.6615070700645447, 1.1547352075576782, 0.7367962598800659, 1.0592544078826904, 0.48621994256973267, 0.6579748392105103, 0.595458984375, 0.9440342783927917, 1.0827107429504395, 1.0706229209899902, 0.3804125189781189, 0.9579113721847534, 0.9907475709915161, 0.6623144149780273, 0.517115592956543, 0.3898656368255615, 0.5884431600570679, 0.7113136649131775, 0.55210280418396, 0.8143147230148315, 0.6042755246162415, 1.4867784976959229, 0.6116529703140259, 0.7994950413703918, 0.4639206528663635, 1.3001998662948608, 0.7065410614013672, 0.4177468419075012, 0.7623780369758606, 0.48920565843582153, 0.6639540195465088, 1.073578119277954, 0.9166761636734009, 0.49030399322509766, 0.37450820207595825, 1.149993658065796, 0.9087821841239929, 0.9789039492607117, 0.794514000415802, 0.5467599630355835, 0.7860501408576965, 0.4639790654182434, 0.8051395416259766, 0.7762530446052551, 0.6899821162223816, 1.1145899295806885, 0.9527756571769714, 1.1382988691329956, 0.3729211390018463, 0.579840362071991, 0.3926572799682617, 0.6421953439712524, 1.1574862003326416, 0.9053859710693359, 1.2011773586273193, 1.3986741304397583, 1.0564825534820557, 0.6901332139968872, 0.7687929272651672, 0.9167767763137817, 0.9780145287513733, 0.7676675915718079, 1.0918771028518677, 1.0945029258728027, 1.2359578609466553, 0.28632429242134094, 1.0085303783416748, 1.1010990142822266, 0.8492262959480286, 0.6476423740386963, 0.7431758046150208, 0.7499859929084778, 0.4834493100643158, 0.9519004821777344, 0.604681670665741, 1.3095275163650513, 0.44762903451919556, 0.9970499277114868, 1.387715220451355, 0.9341044425964355, 1.360653042793274, 0.6169108152389526, 0.741480827331543, 0.87124103307724, 0.8814796805381775, 0.9112734794616699, 1.1314678192138672, 0.7524837851524353, 1.1133017539978027, 117.961669921875, 44.656063079833984, 21.077558517456055, 40.36111068725586, 24.110504150390625, 45.537567138671875, 49.305477142333984, 41.66567611694336, 127.63765716552734, 15.431798934936523, 82.42728424072266, 23.313432693481445, 96.15148162841797, 106.39028930664062, 57.748291015625, 24.58380126953125, 101.5423583984375, 20.253028869628906, 25.2119083404541, 94.06365966796875, 77.97640228271484, 97.44601440429688, 57.59609603881836, 22.705751419067383, 26.39300537109375, 25.30567741394043, 19.49249267578125, 71.321533203125, 23.17961883544922, 90.52129364013672, 91.7074966430664, 171.20176696777344, 41.56156539916992, 99.87267303466797, 69.21499633789062, 86.00042724609375, 55.597957611083984, 28.29806900024414, 98.05208587646484, 57.81170654296875, 24.154394149780273, 60.3324089050293, 110.86050415039062, 56.666717529296875, 30.108734130859375, 54.86269760131836, 14.995890617370605, 28.263668060302734, 81.94692993164062, 34.8572998046875, 31.485570907592773, 33.56585693359375, 95.20049285888672, 102.84697723388672, 33.74275207519531, 90.67642211914062, 66.77810668945312, 103.61747741699219, 47.318328857421875, 51.559814453125, 51.292236328125, 65.4705810546875, 53.51528549194336, 17.073455810546875, 49.53884506225586, 74.6629638671875, 58.36368942260742, 40.41305160522461, 35.132904052734375, 55.9423828125, 89.12413787841797, 28.148099899291992, 57.005531311035156, 49.91082763671875, 120.08497619628906, 109.60623168945312, 34.55119323730469, 20.738134384155273, 74.05105590820312, 148.13047790527344, 78.9381103515625, 93.94012451171875, 20.8981876373291, 60.72633743286133, 20.609130859375, 19.50959587097168, 120.25235748291016, 46.201263427734375, 21.210290908813477, 18.81304931640625, 26.16340446472168, 33.80696105957031, 19.702194213867188, 120.31414794921875, 36.9111328125, 118.02754974365234, 37.4805908203125, 32.1617431640625, 62.212158203125, 35.07258605957031, 40.54409408569336, 25.307743072509766, 130.11366271972656, 28.8662109375, 187.77243041992188, 33.6488037109375, 113.3210220336914, 112.64897918701172, 68.99453735351562, 67.18274688720703, 71.03716278076172, 34.8266487121582, 60.103759765625, 64.17811584472656, 86.82554626464844, 75.96293640136719, 46.43169021606445, 70.47905731201172, 97.45635223388672, 156.37745666503906, 23.507659912109375, 23.688201904296875, 21.656707763671875, 93.28076171875, 28.67506217956543, 55.966121673583984, 14.763214111328125, 51.94216537475586, 146.6488494873047, 53.84235382080078, 70.94277954101562, 20.393218994140625, 29.941162109375, 19.569488525390625, 37.157249450683594, 76.3658447265625, 67.77566528320312, 43.77199935913086, 104.06745910644531, 210.30227661132812, 34.652099609375, 62.68449020385742, 13.994162559509277, 63.52099609375, 53.954647064208984, 49.29608154296875, 96.36409759521484, 110.59941864013672, 19.41600799560547, 116.36388397216797, 48.859920501708984, 56.07861328125, 22.72211456298828, 114.88003540039062, 20.879934310913086, 128.10366821289062, 48.01340866088867, 67.57733154296875, 66.18789672851562, 40.914642333984375, 46.3238525390625, 62.3221549987793, 101.13909912109375, 31.529632568359375, 32.27288818359375, 139.40042114257812, 124.10861206054688, 74.16668701171875, 82.01483154296875, 19.852445602416992, 29.955495834350586, 64.8027114868164, 78.95610809326172, 14.237045288085938, 59.592864990234375, 26.77901840209961, 58.0350227355957, 34.30202865600586, 17.251529693603516, 67.07487487792969, 52.9674072265625, 45.874603271484375, 22.259368896484375, 100.86782836914062, 22.56658935546875, 58.3494873046875, 32.369651794433594, 19.773834228515625, 50.41880798339844, 63.24592590332031, 56.08350372314453, 41.629852294921875, 61.016204833984375, 62.677406311035156, 69.59835815429688, 22.897783279418945, 143.9991912841797, 54.99905014038086, 85.19326782226562, 60.73781967163086, 35.76353454589844, 27.941070556640625, 52.87128829956055, 18.04295539855957, 81.21112060546875, 24.515077590942383, 17.02825927734375, 51.73324966430664, 17.998727798461914, 19.380218505859375, 82.10640716552734, 18.70370101928711, 17.591737747192383, 52.66230392456055, 16.870685577392578, 158.01666259765625, 96.96942138671875, 46.679359436035156, 97.42603302001953, 29.7698974609375, 223.2322235107422, 77.0824966430664, 48.39761734008789, 17.514347076416016, 99.11568450927734, 103.1369400024414, 24.864286422729492, 70.84234619140625, 87.90415954589844, 160.30856323242188, 26.155229568481445, 26.455078125, 122.57526397705078, 58.8797607421875, 97.81281280517578, 84.08036041259766, 15.564682006835938, 29.872501373291016, 106.72881317138672, 74.63422393798828, 18.21539306640625, 86.06071472167969, 87.30192565917969, 64.99411010742188, 186.9967498779297, 27.58560562133789, 26.104013442993164, 55.68518829345703, 105.7034912109375, 14.826416015625, 99.60427856445312, 59.945068359375, 131.75320434570312, 79.43118286132812, 40.89030456542969, 119.83016967773438, 135.55491638183594, 51.71052551269531, 29.444093704223633, 56.97673034667969, 36.74580001831055, 22.98759651184082, 71.13296508789062, 16.37942886352539, 28.5489501953125, 81.07473754882812, 17.233179092407227, 42.798065185546875, 32.034149169921875, 9.069000244140625, 38.6938591003418, 143.06600952148438, 103.6151123046875, 18.054290771484375, 131.64447021484375, 51.192626953125, 17.006805419921875, 28.19938087463379, 56.62929153442383, 88.79554748535156, 13.665558815002441, 25.93685531616211, 164.56370544433594, 74.75759887695312, 48.03847885131836, 34.06707763671875, 114.29974365234375, 42.800010681152344, 122.38638305664062, 19.66180419921875, 24.151996612548828, 83.3293228149414, 23.520082473754883, 33.589111328125, 92.19400024414062, 88.6943359375, 105.23860931396484, 28.131689071655273, 16.165008544921875, 39.82666015625, 1.8983477354049683, 2.5934059619903564, 1.8873226642608643, 1.2611570358276367, 3.122576951980591, 3.4957520961761475, 3.0794460773468018, 2.9931881427764893, 1.8003281354904175, 1.0479779243469238, 2.6684837341308594, 2.6456968784332275, 0.9479650855064392, 1.3786065578460693, 1.4401825666427612, 1.8644875288009644, 2.5880894660949707, 2.449364185333252, 1.7754621505737305, 3.1631577014923096, 2.19283390045166, 3.3032302856445312, 2.3295907974243164, 1.4086904525756836, 2.576648235321045, 1.9453306198120117, 1.7703161239624023, 1.837929606437683, 1.0856122970581055, 1.316401481628418, 2.2124929428100586, 1.8397051095962524, 1.6496737003326416, 1.75536048412323, 2.325073003768921, 1.1470947265625, 1.9621881246566772, 2.4762609004974365, 2.3617982864379883, 2.2146425247192383, 1.8977364301681519, 1.344710350036621, 2.400773048400879, 1.6906156539916992, 3.0373430252075195, 1.780623435974121, 1.9263442754745483, 2.3283188343048096, 1.3814517259597778, 2.5336062908172607, 2.5145957469940186, 3.0121498107910156, 1.6274508237838745, 2.0730397701263428, 2.0216526985168457, 1.8160027265548706, 1.657126784324646, 3.2981393337249756, 2.378906011581421, 2.846515417098999, 1.9846161603927612, 2.419926643371582, 1.9215123653411865, 2.230212450027466, 2.584362745285034, 2.0120222568511963, 2.299300193786621, 2.710345506668091, 1.0369443893432617, 1.7427630424499512, 1.3162879943847656, 1.7408475875854492, 2.4691383838653564, 1.7895864248275757, 1.9377150535583496, 1.8706847429275513, 2.8685314655303955, 1.4194735288619995, 1.6530367136001587, 2.573765754699707, 2.1434438228607178, 1.4805952310562134, 3.361485004425049, 2.6437313556671143, 2.6318156719207764, 2.0381343364715576, 2.159224510192871, 2.8722641468048096, 3.050349712371826, 1.395228385925293, 2.9291605949401855, 1.619515299797058, 2.6071529388427734, 2.8813488483428955, 1.564566969871521, 1.3291937112808228, 2.125704765319824, 2.812764883041382, 2.5132269859313965, 2.22580623626709, 1.804616093635559, 1.9879491329193115, 1.6506452560424805, 2.556929349899292, 2.6068921089172363, 1.685603141784668, 2.0314888954162598, 1.7016031742095947, 2.6357951164245605, 1.798792839050293, 1.3827085494995117, 1.7750463485717773, 2.9524571895599365, 2.6831982135772705, 2.172321319580078, 2.9279143810272217, 3.821828603744507, 4.067358016967773, 2.712700366973877, 2.841820001602173, 1.5529966354370117, 2.4491751194000244, 2.5216264724731445, 2.276726722717285, 1.7251691818237305, 2.771259069442749, 1.762439250946045, 3.184964179992676, 3.199418306350708, 2.2393975257873535, 1.277607798576355, 2.6631839275360107, 2.3160414695739746, 1.811832070350647, 1.8436516523361206, 2.947032928466797, 1.7947918176651, 1.6049813032150269, 1.4928268194198608, 1.354537010192871, 1.3507553339004517, 3.0184361934661865, 1.7596312761306763, 2.8481390476226807, 2.311732530593872, 1.766467809677124, 2.919297695159912, 1.8984955549240112, 1.874903678894043, 2.923443555831909, 1.7938756942749023, 1.657784342765808, 1.5800074338912964, 3.0533952713012695, 2.7771599292755127, 1.2731292247772217, 2.426469564437866, 1.3252575397491455, 1.988814353942871, 1.2120612859725952, 2.379373788833618, 1.9540139436721802, 3.587836265563965, 3.1212687492370605, 1.3313930034637451, 2.2942607402801514, 1.9859362840652466, 3.815790891647339, 2.797196626663208, 1.2600696086883545, 2.344801187515259, 1.6846952438354492, 2.4038305282592773, 0.9999975562095642, 1.8018239736557007, 1.899839162826538, 2.674238920211792, 1.5491036176681519, 3.025545597076416, 2.2800111770629883, 1.8140592575073242, 1.5995436906814575, 2.134993553161621, 2.787095308303833, 2.343085289001465, 1.9884099960327148, 3.31579327583313, 2.0973730087280273, 2.5368940830230713, 2.9476044178009033, 3.047499895095825, 1.8119137287139893, 1.6835144758224487, 2.22580623626709, 2.6915314197540283, 2.679546356201172, 1.5363943576812744, 2.3205060958862305, 2.3255817890167236, 2.4627621173858643, 2.4818849563598633, 1.806069254875183, 3.091655731201172, 2.714282274246216, 2.013622999191284, 1.9946717023849487, 2.5349326133728027, 2.6142539978027344, 2.8702456951141357, 1.4937946796417236, 3.2027676105499268, 1.9156848192214966, 3.1696224212646484, 2.142939805984497, 1.777695894241333, 2.3929052352905273, 2.965047836303711, 3.109031915664673, 2.0812292098999023, 1.1991262435913086, 2.1863508224487305, 1.4315918684005737, 2.6737704277038574, 2.35604190826416, 2.333400011062622, 1.7240341901779175, 3.415626049041748, 1.6962652206420898, 2.53216552734375, 2.04656982421875, 2.494157552719116, 2.7485156059265137, 3.1037144660949707, 2.668590545654297, 3.550335645675659, 2.6819534301757812, 3.063952684402466, 1.0382909774780273, 2.9661476612091064, 3.00152325630188, 2.596510648727417, 2.272047758102417, 2.2536346912384033, 2.410552978515625, 2.777543306350708, 2.0634255409240723, 1.8589162826538086, 2.4020605087280273, 1.7728699445724487, 2.5969228744506836, 1.6400779485702515, 1.9516266584396362, 2.3819169998168945, 2.1515512466430664, 2.4167778491973877, 1.5579922199249268, 2.745492696762085, 1.8512296676635742, 1.7617326974868774, 2.2858211994171143, 3.1083908081054688, 2.4303805828094482, 2.349663734436035, 2.4206361770629883, 2.584393262863159, 2.660637855529785, 1.319753646850586, 2.8115756511688232, 2.2309770584106445, 1.993203043937683, 2.7437047958374023, 2.9821078777313232, 1.932534098625183, 2.2168257236480713, 3.019122838973999, 2.4245922565460205, 1.7659246921539307, 2.7703030109405518, 1.7433825731277466, 2.0381979942321777, 2.8092315196990967, 2.874424934387207, 1.7255524396896362, 2.044135093688965, 1.1803358793258667, 1.9417524337768555, 2.847705125808716, 3.9133336544036865, 1.9043688774108887, 1.4612760543823242, 2.1179380416870117, 1.9206725358963013, 1.5442609786987305, 2.4972071647644043, 2.6380059719085693, 3.489488124847412, 1.9848393201828003, 1.7773767709732056, 2.6799983978271484, 1.927876353263855, 0.12728078663349152, 0.1362343430519104, 0.09872736036777496, 0.10623189806938171, 0.06984467059373856, 0.14094483852386475, 0.12410531938076019, 0.14012402296066284, 0.1268213391304016, 0.10256045311689377, 0.14996585249900818, 0.08267375081777573, 0.08084096759557724, 0.17593809962272644, 0.16503439843654633, 0.16869325935840607, 0.10188379138708115, 0.12777924537658691, 0.11906128376722336, 0.06333845853805542, 0.11633377522230148, 0.12024635076522827, 0.14667393267154694, 0.11088170111179352, 0.13058632612228394, 0.15842944383621216, 0.0761808380484581, 0.11054746061563492, 0.07155688107013702, 0.10040170699357986, 0.12197154760360718, 0.09188362210988998, 0.0869542732834816, 0.21959899365901947, 0.09223975986242294, 0.08971453458070755, 0.15498249232769012, 0.11909663677215576, 0.17680387198925018, 0.1598106473684311, 0.22227247059345245, 0.1572841852903366, 0.1096373125910759, 0.14934222400188446, 0.09238065779209137, 0.107089564204216, 0.11196160316467285, 0.11491872370243073, 0.14862293004989624, 0.1398008018732071, 0.14056693017482758, 0.10425323247909546, 0.12200397253036499, 0.11184828728437424, 0.1199980303645134, 0.07493326812982559, 0.1119694784283638, 0.07994058728218079, 0.08931023627519608, 0.07717819511890411, 0.15133512020111084, 0.13599133491516113, 0.1868049055337906, 0.08503454923629761, 0.10186910629272461, 0.1384229063987732, 0.131825253367424, 0.14113843441009521, 0.07815837860107422, 0.11000093817710876, 0.06611725687980652, 0.12822766602039337, 0.12145497649908066, 0.16486747562885284, 0.13066117465496063, 0.12161889672279358, 0.14860105514526367, 0.10332462936639786, 0.12832164764404297, 0.10373520851135254, 0.0898669883608818, 0.15909232199192047, 0.08884011954069138, 0.1498202681541443, 0.09389882534742355, 0.1644921898841858, 0.1598176807165146, 0.061901357024908066, 0.09845007956027985, 0.023883409798145294, 0.17821216583251953, 0.14789481461048126, 0.030522646382451057, 0.11210805922746658, 0.12064123898744583, 0.1982637196779251, 0.12329050153493881, 0.12002498656511307, 0.09738688915967941, 0.11468593031167984, 0.09721922874450684, 0.14250634610652924, 0.06862404942512512, 0.07327573746442795, 0.10054473578929901, 0.10012365132570267, 0.08832941204309464, 0.2237337827682495, 0.13993225991725922, 0.14123734831809998, 0.12481286376714706, 0.1881725788116455, 0.12906986474990845, 0.1153702363371849, 0.07453085482120514, 0.07567568868398666, 0.14162279665470123, 0.06030815839767456, 0.10400613397359848, 0.11038634926080704, 0.10150914639234543, 0.10526254773139954, 0.09376262128353119, 0.1791738122701645, 0.1232718825340271, 0.0946425348520279, 0.14515718817710876, 0.09572572261095047, 0.11673018336296082, 0.07376253604888916, 0.11385255306959152, 0.09083551168441772, 0.17531074583530426, 0.10757988691329956, 0.16838422417640686, 0.11657480895519257, 0.10821323841810226, 0.0887831300497055, 0.055050190538167953, 0.15508362650871277, 0.13705061376094818, 0.141739621758461, 0.1309165358543396, 0.11963177472352982, 0.17318926751613617, 0.14807307720184326, 0.09574689716100693, 0.14655767381191254, 0.06516988575458527, 0.13510166108608246, 0.178214430809021, 0.12950223684310913, 0.1450362503528595, 0.10473048686981201, 0.1925550103187561, 0.0732569471001625, 0.11469562351703644, 0.11211207509040833, 0.13532623648643494, 0.11928689479827881, 0.10027611255645752, 0.1645929366350174, 0.13873286545276642, 0.12385060638189316, 0.1069294884800911, 0.22859692573547363, 0.10027335584163666, 0.09944834560155869, 0.1284596025943756, 0.04890262335538864, 0.12219903618097305, 0.08172909915447235, 0.1347832977771759, 0.18927498161792755, 0.12499698996543884, 0.07978977262973785, 0.08154552429914474, 0.14706918597221375, 0.17361152172088623, 0.13012781739234924, 0.08312162011861801, 0.141700878739357, 0.13831405341625214, 0.09883439540863037, 0.16578131914138794, 0.15599574148654938, 0.09187743067741394, 0.08941490203142166, 0.16013002395629883, 0.12037400901317596, 0.1643885374069214, 0.19910965859889984, 0.07354849576950073, 0.07518784701824188, 0.07038891315460205, 0.06309765577316284, 0.080617256462574, 0.10943124443292618, 0.08160221576690674, 0.1621243953704834, 0.11817868798971176, 0.11725650727748871, 0.06467967480421066, 0.13724248111248016, 0.11216166615486145, 0.1128465086221695, 0.14598722755908966, 0.09826982021331787, 0.12246255576610565, 0.10591349005699158, 0.08369932323694229, 0.1333690583705902, 0.08944026380777359, 0.07491576671600342, 0.10593120008707047, 0.11064989119768143, 0.16048747301101685, 0.19199024140834808, 0.1101069450378418, 0.11718352884054184, 0.12280251830816269, 0.14019174873828888, 0.12007778137922287, 0.12611933052539825, 0.18793781101703644, 0.13658207654953003, 0.08652443438768387, 0.11803334951400757, 0.13347315788269043, 0.09785108268260956, 0.11854774504899979, 0.09398851543664932, 0.15379492938518524, 0.09863967448472977, 0.09233716875314713, 0.11613680422306061, 0.12829375267028809, 0.04884830862283707, 0.027902083471417427, 0.07923897355794907, 0.08778218924999237, 0.14623327553272247, 0.12769027054309845, 0.04593997076153755, 0.10646242648363113, 0.14607718586921692, 0.06780508905649185, 0.07402104139328003, 0.18249396979808807, 0.08765023946762085, 0.15130257606506348, 0.21889925003051758, 0.10435748100280762, 0.16315098106861115, 0.13674414157867432, 0.09961139410734177, 0.14905042946338654, 0.15906740725040436, 0.14864283800125122, 0.07910911738872528, 0.14898806810379028, 0.12293374538421631, 0.16765160858631134, 0.07605989277362823, 0.039560578763484955, 0.0545235238969326, 0.053811606019735336, 0.10434918850660324, 0.06666276603937149, 0.10998086631298065, 0.11690719425678253, 0.14541928470134735, 0.07716112583875656, 0.11576753109693527, 0.17357932031154633, 0.05953900143504143, 0.11695998907089233, 0.13433408737182617, 0.14024481177330017, 0.1067996546626091, 0.07575680315494537, 0.1326097846031189, 0.08954787999391556, 0.04885917901992798, 0.11169975996017456, 0.10199616849422455, 0.06338845193386078, 0.08840864151716232, 0.21140919625759125, 0.09638459980487823, 0.11418436467647552, 0.09438647329807281, 0.10756083577871323, 0.08691989630460739, 0.11861924827098846, 0.08533290773630142, 0.18841321766376495, 0.094416044652462, 0.1698569804430008, 0.15357352793216705, 1.0296635627746582, 0.8782564997673035, 1.1831669807434082, 0.4132910966873169, 0.7257604598999023, 1.0652085542678833, 1.0912182331085205, 0.9361820220947266, 0.7909151911735535, 1.437878966331482, 0.6974841356277466, 1.2193270921707153, 0.643717348575592, 0.592332124710083, 0.5194498300552368, 0.9417686462402344, 0.6904698610305786, 0.3297365605831146, 0.8226701021194458, 0.7168353199958801, 1.4064489603042603, 0.5106277465820312, 0.9350504875183105, 0.8933175206184387, 1.083396553993225, 0.8724064230918884, 1.0524840354919434, 0.8720411658287048, 0.5405593514442444, 0.6756547689437866, 1.0893489122390747, 1.0331928730010986, 0.23925583064556122, 0.909074604511261, 0.47662660479545593, 0.5844696164131165, 0.5982879996299744, 0.6481279134750366, 0.7810404896736145, 0.9200699925422668, 1.0891776084899902, 1.097583293914795, 0.8603118062019348, 0.41868406534194946, 0.9183127880096436, 0.8900802135467529, 0.5806840658187866, 0.9026634097099304, 1.8605272769927979, 0.573613166809082, 0.760223388671875, 0.8054249286651611, 1.5196832418441772, 0.8682981729507446, 0.8435746431350708, 0.8295010328292847, 0.91456538438797, 1.1310182809829712, 0.7786266803741455, 1.0788534879684448, 0.8301997184753418, 0.481363981962204, 1.1600087881088257, 0.451656699180603, 0.8619992136955261, 0.799763023853302, 0.6449869275093079, 0.5962442755699158, 0.37876036763191223, 1.2517021894454956, 0.5765284895896912, 1.0315083265304565, 1.053419828414917, 1.2738521099090576, 0.6242056488990784, 0.658515453338623, 0.9119274616241455, 0.6495568156242371, 0.9047778248786926, 0.6623318195343018, 0.6976469159126282, 1.1061444282531738, 0.5663459300994873, 0.7185524702072144, 0.8970677256584167, 0.5162572264671326, 0.9360960125923157, 1.1557823419570923, 0.6563298106193542, 1.2137078046798706, 0.829791247844696, 0.9071010947227478, 0.7808037996292114, 0.9038805961608887, 1.3338804244995117, 0.9040911793708801, 0.6824526786804199, 0.7255839109420776, 1.1455063819885254, 0.3164580166339874, 0.7905710339546204, 0.4730813503265381, 0.9751647114753723, 0.7803813219070435, 0.7629237174987793, 0.7176429629325867, 0.790399968624115, 1.0955636501312256, 1.0039445161819458, 0.47727590799331665, 0.8264428377151489, 1.033921480178833, 0.640070378780365, 0.7358726859092712, 0.8192682266235352, 0.678941011428833, 0.9755274653434753, 0.40385690331459045, 0.8180519938468933, 0.8843684196472168, 1.3760430812835693, 0.7344254851341248, 1.0536704063415527, 0.6309291124343872, 0.9029031991958618, 0.2772374451160431, 1.436920404434204, 0.9490635395050049, 1.0171656608581543, 1.1404070854187012, 0.5544738173484802, 0.43958744406700134, 0.6914101839065552, 0.7963210940361023, 1.0325655937194824, 0.7241917848587036, 1.059160590171814, 1.0709829330444336, 0.9981657266616821, 0.8422985076904297, 0.8618649244308472, 0.5413890480995178, 0.7901214957237244, 0.5352307558059692, 0.5933061838150024, 0.4982236325740814, 1.132138729095459, 0.6013990640640259, 0.6279453635215759, 0.5188096761703491, 0.9540951251983643, 0.9767295718193054, 0.5263879299163818, 0.44023239612579346, 0.33130431175231934, 0.7952020168304443, 0.8501399755477905, 0.7536134123802185, 0.899859607219696, 0.6713047027587891, 0.6420512199401855, 0.7738819122314453, 1.2973792552947998, 0.4379579722881317, 0.7579142451286316, 1.2657384872436523, 0.7119218111038208, 0.7911762595176697, 1.1080483198165894, 1.7361587285995483, 0.7971949577331543, 0.4838794469833374, 0.6002551317214966, 0.8359143137931824, 0.720470666885376, 1.1052803993225098, 0.671710193157196, 0.8818781971931458, 1.1848278045654297, 1.165667176246643, 1.4570658206939697, 0.5957812070846558, 0.9543601870536804, 0.9000914692878723, 0.8751010894775391, 0.32613974809646606, 0.3260137140750885, 1.0716352462768555, 0.7225707173347473, 0.7395267486572266, 0.601319432258606, 0.9095112681388855, 0.9883976578712463, 0.6964712142944336, 0.6288504600524902, 0.5641937255859375, 1.0442991256713867, 1.1565992832183838, 0.49103179574012756, 0.8092079162597656, 0.8267386555671692, 1.2156476974487305, 0.7439366579055786, 1.2570351362228394, 0.8942436575889587, 0.8545361757278442, 1.0729330778121948, 0.7399390339851379, 0.7165992856025696, 0.6388360261917114, 0.7973240613937378, 1.6289774179458618, 1.0599040985107422, 0.8111599683761597, 0.9823452830314636, 0.6851335167884827, 1.0752722024917603, 0.9510940909385681, 1.1309045553207397, 0.6090230345726013, 0.8407389521598816, 0.638433039188385, 0.9591566324234009, 1.163718342781067, 0.7106214761734009, 0.9814375042915344, 0.7685233950614929, 0.6077235341072083, 0.9384335279464722, 0.664000391960144, 1.0876531600952148, 0.6288809776306152, 1.239216685295105, 0.7417899370193481, 0.6691659688949585, 0.5192959308624268, 0.5177750587463379, 0.6018403172492981, 1.1796833276748657, 0.5731983780860901, 0.8958209753036499, 0.7456768155097961, 1.0654897689819336, 1.242576241493225, 0.5666965842247009, 1.0308518409729004, 0.7107947468757629, 0.5188567638397217, 0.3887350261211395, 0.7922759652137756, 0.6720200181007385, 1.1129180192947388, 0.7311239242553711, 0.9756917953491211, 0.9524192810058594, 1.2557522058486938, 0.9538317918777466, 0.3884510099887848, 0.8290568590164185, 1.0801215171813965, 0.6592301726341248, 0.9140947461128235, 1.0037413835525513, 1.1303086280822754, 1.2346265316009521, 0.9724108576774597, 0.7091901302337646, 1.0846837759017944, 0.9136350750923157, 0.6146586537361145, 1.0868691205978394, 0.84085613489151, 0.9199522137641907, 0.7497970461845398, 0.6945733428001404, 0.4729066491127014, 0.6765477061271667, 1.1566319465637207, 0.9543850421905518, 0.649240255355835, 0.5962783098220825, 0.8901509046554565, 0.5091626644134521, 0.4904041886329651, 0.6118422746658325, 0.8776739239692688, 0.937048077583313, 0.616619348526001, 1.08095121383667, 0.5934231281280518, 0.8415800929069519, 1.3731844425201416, 0.5523444414138794, 0.7677937746047974, 0.567333459854126, 0.305616557598114, 0.6009193062782288, 0.9244404435157776, 0.6326747536659241, 0.49300017952919006, 80.11639404296875, 32.259735107421875, 67.71971893310547, 58.72096633911133, 18.030723571777344, 22.0509033203125, 36.693965911865234, 134.5174560546875, 12.544158935546875, 21.33688735961914, 18.013580322265625, 51.688201904296875, 68.2791748046875, 20.718994140625, 38.14646911621094, 32.836448669433594, 88.88369750976562, 97.6522445678711, 25.616840362548828, 36.82705307006836, 37.831809997558594, 72.98422241210938, 51.49878692626953, 17.532501220703125, 45.40884780883789, 25.112838745117188, 73.87504577636719, 27.472030639648438, 113.964599609375, 58.69997787475586, 63.13325500488281, 78.05975341796875, 59.05419921875, 24.925058364868164, 24.395721435546875, 17.355575561523438, 60.5899658203125, 125.15365600585938, 74.2359848022461, 47.93276596069336, 67.35787963867188, 72.78463745117188, 55.40949249267578, 120.37076568603516, 22.94654655456543, 33.10113525390625, 26.483078002929688, 92.40074157714844, 70.07939147949219, 86.23906707763672, 18.317506790161133, 35.25556945800781, 42.047611236572266, 74.39363098144531, 37.59065246582031, 82.53617095947266, 37.33511734008789, 79.97378540039062, 110.12420654296875, 45.336883544921875, 94.95064544677734, 18.981109619140625, 115.0204849243164, 52.8822021484375, 40.77642822265625, 40.40359115600586, 42.19892501831055, 59.76762390136719, 83.02083587646484, 33.480712890625, 36.77460479736328, 82.83622741699219, 62.41471481323242, 62.79559326171875, 26.3702392578125, 63.40543746948242, 24.8310546875, 38.579795837402344, 57.798309326171875, 46.56989669799805, 21.736181259155273, 30.792104721069336, 115.59542846679688, 19.8583984375, 41.627742767333984, 44.661468505859375, 61.83888626098633, 58.557918548583984, 43.47528076171875, 38.681549072265625, 68.70978546142578, 71.3289566040039, 33.407875061035156, 79.2794189453125, 22.106571197509766, 81.8742446899414, 110.37507629394531, 210.85061645507812, 171.3782958984375, 145.55235290527344, 22.988561630249023, 22.44317626953125, 171.80792236328125, 33.1971435546875, 60.17352294921875, 28.720062255859375, 39.099609375, 146.75140380859375, 86.47378540039062, 19.661136627197266, 98.06881713867188, 22.203277587890625, 107.2179946899414, 51.930633544921875, 80.71920013427734, 17.41309928894043, 96.49835968017578, 31.31764030456543, 137.19345092773438, 70.88290405273438, 15.614175796508789, 171.83447265625, 75.54878997802734, 143.01199340820312, 35.02090072631836, 57.22117233276367, 53.08181381225586, 29.21796989440918, 85.99495697021484, 71.4264907836914, 45.72818374633789, 47.21389389038086, 71.056396484375, 88.43087768554688, 129.69406127929688, 53.86083984375, 100.9052505493164, 90.72315979003906, 75.54714965820312, 63.52187728881836, 20.79833984375, 34.08348083496094, 23.601343154907227, 65.65487670898438, 77.70100402832031, 22.101076126098633, 29.305877685546875, 50.497528076171875, 114.34162139892578, 24.752777099609375, 39.81033706665039, 64.13457489013672, 23.222015380859375, 18.59356689453125, 16.12968635559082, 28.9955997467041, 30.834970474243164, 41.33416748046875, 84.76349639892578, 26.52341651916504, 27.58404541015625, 52.51675033569336, 73.5732192993164, 36.13711929321289, 22.416461944580078, 103.14813232421875, 32.32325744628906, 94.5848388671875, 74.39276123046875, 64.87671661376953, 176.77734375, 38.25372314453125, 43.202606201171875, 45.050018310546875, 33.055908203125, 59.70242691040039, 24.738250732421875, 15.61644458770752, 30.91925048828125, 147.21629333496094, 16.15777587890625, 54.91543960571289, 24.88067626953125, 28.33575439453125, 85.01937103271484, 159.70953369140625, 37.79153060913086, 109.49896240234375, 23.76092529296875, 114.13446044921875, 27.190824508666992, 170.86253356933594, 72.7843017578125, 17.04022216796875, 64.22262573242188, 44.71844482421875, 44.025691986083984, 62.318172454833984, 170.5721435546875, 20.06131935119629, 102.83507537841797, 20.10947036743164, 103.04534912109375, 29.928476333618164, 22.03961181640625, 33.00820541381836, 104.24755859375, 57.96680450439453, 33.38883590698242, 136.466796875, 141.19256591796875, 44.80265426635742, 72.21524047851562, 22.831268310546875, 33.656463623046875, 120.85678100585938, 45.098182678222656, 84.41570281982422, 78.83059692382812, 31.70159912109375, 119.26724243164062, 41.01776123046875, 21.556640625, 88.27948760986328, 89.12709045410156, 82.79046630859375, 62.51525115966797, 17.8663330078125, 52.02395248413086, 27.75152587890625, 22.898916244506836, 41.414306640625, 17.515777587890625, 50.37356185913086, 128.54302978515625, 46.765472412109375, 111.04425811767578, 91.39154052734375, 132.7435302734375, 22.98157501220703, 73.26968383789062, 27.763490676879883, 57.339202880859375, 48.842376708984375, 50.38540267944336, 22.581571578979492, 65.5091323852539, 18.24285888671875, 91.60177612304688, 23.78826904296875, 94.03006744384766, 16.121191024780273, 104.58849334716797, 53.00442123413086, 22.64495849609375, 15.06341552734375, 23.61756706237793, 22.94829559326172, 52.489501953125, 64.06654357910156, 17.239728927612305, 43.02545928955078, 116.66073608398438, 19.23371124267578, 74.01848602294922, 28.387285232543945, 65.32244110107422, 74.34627532958984, 94.2303466796875, 30.596702575683594, 25.2491455078125, 40.74770736694336, 79.77761840820312, 169.29632568359375, 85.25875091552734, 31.477767944335938, 64.26786804199219, 18.2969970703125, 33.845703125, 18.526721954345703, 35.582969665527344, 19.46839714050293, 39.09183120727539, 54.40205001831055, 57.62980270385742, 20.80572509765625, 50.19948959350586, 30.70931625366211, 64.83094787597656, 70.42831420898438, 56.48355484008789, 48.357513427734375, 91.3890380859375, 14.814719200134277, 81.10527801513672, 65.60027313232422, 81.83820343017578, 41.06862258911133, 37.790367126464844, 91.12651824951172, 2.5065951347351074, 2.884782075881958, 1.7650612592697144, 2.2275848388671875, 3.229295015335083, 3.197206974029541, 1.5959564447402954, 1.0808706283569336, 1.7612087726593018, 1.760903239250183, 2.6775734424591064, 2.446660041809082, 2.357926368713379, 2.074282169342041, 1.4281281232833862, 2.154249429702759, 2.258991241455078, 1.5022064447402954, 1.729358196258545, 2.0600874423980713, 2.0415828227996826, 2.152041435241699, 1.4783295392990112, 3.2221133708953857, 1.9485207796096802, 1.562172770500183, 1.2523411512374878, 2.4975650310516357, 2.0529661178588867, 2.26300048828125, 2.096194267272949, 2.229576349258423, 1.5207644701004028, 1.7198972702026367, 2.8743417263031006, 2.3694581985473633, 1.55474853515625, 1.499853491783142, 3.021252393722534, 2.260648250579834, 2.1495676040649414, 2.5837419033050537, 1.8126258850097656, 2.4300014972686768, 3.968886375427246, 2.2529823780059814, 2.4077844619750977, 2.788094997406006, 2.3617444038391113, 1.749123215675354, 2.002763509750366, 1.8736733198165894, 1.8401778936386108, 2.5976555347442627, 2.458652973175049, 1.2085294723510742, 1.7279996871948242, 1.239155888557434, 3.497321367263794, 1.902687668800354, 2.699857234954834, 2.2458009719848633, 1.8973802328109741, 2.667720079421997, 2.61729097366333, 1.7233201265335083, 2.6673290729522705, 2.088798999786377, 2.6370768547058105, 1.989707350730896, 2.117342948913574, 2.066460609436035, 2.637467622756958, 2.7662248611450195, 1.8741872310638428, 2.15517520904541, 1.5232807397842407, 1.8567456007003784, 2.887664794921875, 2.2251155376434326, 1.8184499740600586, 3.0081138610839844, 2.4752163887023926, 2.263181209564209, 2.40222430229187, 1.4738105535507202, 2.7225353717803955, 2.441006660461426, 1.7228612899780273, 1.836121678352356, 1.7493942975997925, 1.9112671613693237, 1.9185057878494263, 2.367281913757324, 3.0167791843414307, 1.1549614667892456, 2.5837128162384033, 2.398336172103882, 1.6195220947265625, 2.318929433822632, 2.565032958984375, 1.8947629928588867, 1.8947384357452393, 2.166879177093506, 2.7203097343444824, 1.8286778926849365, 2.414005756378174, 2.027554512023926, 2.5151050090789795, 2.442835569381714, 2.544783353805542, 2.5034332275390625, 2.641700267791748, 1.5494046211242676, 1.663661003112793, 2.4127743244171143, 3.183339834213257, 2.3399744033813477, 2.062182664871216, 1.789052128791809, 1.6465957164764404, 2.6122829914093018, 2.0108988285064697, 1.4804372787475586, 1.5996007919311523, 2.9965221881866455, 1.3540352582931519, 1.9518461227416992, 3.258519172668457, 2.825857162475586, 3.5340147018432617, 2.783453941345215, 2.2798032760620117, 1.3636645078659058, 2.093686580657959, 2.8783562183380127, 1.571730136871338, 2.362482786178589, 2.9473156929016113, 1.8505020141601562, 2.004063606262207, 1.7262213230133057, 2.043288469314575, 2.0207784175872803, 2.179995536804199, 2.8052003383636475, 2.034938097000122, 3.630601167678833, 3.0199458599090576, 2.218539237976074, 1.7943830490112305, 1.6418571472167969, 1.4748711585998535, 3.0372653007507324, 2.403414487838745, 2.6682188510894775, 1.8885068893432617, 1.9709701538085938, 2.974116086959839, 2.5309996604919434, 1.0860967636108398, 1.4861788749694824, 2.2758724689483643, 2.349191904067993, 1.9263362884521484, 1.8581589460372925, 1.5701565742492676, 3.0040178298950195, 2.1935510635375977, 1.135771632194519, 3.089764356613159, 2.018305778503418, 2.169325828552246, 2.205888271331787, 1.8068445920944214, 1.1745058298110962, 2.310765266418457, 1.1455161571502686, 2.7449004650115967, 1.3126651048660278, 2.0763096809387207, 2.1381750106811523, 1.8196630477905273, 2.1083195209503174, 1.9154372215270996, 2.526883840560913, 3.0861237049102783, 2.303074836730957, 1.209181547164917, 2.1829044818878174, 2.1096200942993164, 1.880942702293396, 2.214022636413574, 1.7163076400756836, 1.7411545515060425, 1.4761399030685425, 3.5420336723327637, 1.889242172241211, 1.9567675590515137, 1.5762606859207153, 2.973684310913086, 1.5003423690795898, 2.275933265686035, 1.543298602104187, 1.6163053512573242, 2.8645498752593994, 1.3186733722686768, 2.8372020721435547, 1.8172008991241455, 3.425023078918457, 2.31955623626709, 2.245424509048462, 1.8438767194747925, 1.9359731674194336, 1.7021517753601074, 1.8267529010772705, 2.096919059753418, 2.1263914108276367, 2.108536720275879, 2.894953489303589, 2.852839231491089, 1.2590620517730713, 1.4902502298355103, 2.54217791557312, 1.9465242624282837, 2.70577335357666, 2.146312952041626, 3.376559257507324, 2.2783584594726562, 1.631978154182434, 1.3362497091293335, 2.2140541076660156, 1.7560001611709595, 1.1205588579177856, 2.4060657024383545, 2.752258777618408, 1.580866813659668, 2.365323066711426, 1.6749449968338013, 2.804988145828247, 3.161076784133911, 3.269723653793335, 2.5976507663726807, 2.6559667587280273, 2.1531901359558105, 3.0557453632354736, 2.648456335067749, 1.3111664056777954, 1.3943222761154175, 3.114699602127075, 2.5306100845336914, 2.6532084941864014, 3.0495762825012207, 2.6154165267944336, 1.4685369729995728, 2.3511972427368164, 1.928654432296753, 1.5126919746398926, 1.7690247297286987, 1.6911330223083496, 2.640608787536621, 2.402907371520996, 1.4432411193847656, 2.196352958679199, 2.929497718811035, 2.7146706581115723, 1.9301706552505493, 2.288489580154419, 1.7249573469161987, 2.9239721298217773, 1.9153716564178467, 1.8722885847091675, 2.309079170227051, 2.414911985397339, 1.79857337474823, 2.1182074546813965, 2.6892809867858887, 2.3074300289154053, 3.301378011703491, 2.988593101501465, 2.055305242538452, 1.7261933088302612, 2.384772300720215, 1.7335643768310547, 1.2916382551193237, 2.323930501937866, 2.9040255546569824, 2.093926429748535, 1.067270278930664, 3.0803380012512207, 1.8462233543395996, 1.7678254842758179, 1.8567368984222412, 2.7879350185394287, 2.0472183227539062, 3.2467198371887207, 2.0157861709594727, 1.700753092765808, 1.7368650436401367, 2.284396171569824, 0.2195798009634018, 0.1479121595621109, 0.07465152442455292, 0.14827404916286469, 0.1060732826590538, 0.18963885307312012, 0.10664420574903488, 0.1532651036977768, 0.08419132232666016, 0.11985581368207932, 0.16289366781711578, 0.21506047248840332, 0.08472052216529846, 0.0888897180557251, 0.11932077258825302, 0.10602804273366928, 0.15468855202198029, 0.14691445231437683, 0.10248686373233795, 0.1365351527929306, 0.14550179243087769, 0.0883994847536087, 0.14292696118354797, 0.08093320578336716, 0.1260015219449997, 0.1609298288822174, 0.061842773109674454, 0.1424611657857895, 0.09037148952484131, 0.12638039886951447, 0.18388648331165314, 0.10689172148704529, 0.13296440243721008, 0.10382314771413803, 0.1029461994767189, 0.1194133386015892, 0.16265186667442322, 0.07056772708892822, 0.11981851607561111, 0.13142962753772736, 0.14430581033229828, 0.11250437796115875, 0.16668036580085754, 0.17935387790203094, 0.10172879695892334, 0.16380733251571655, 0.08775347471237183, 0.09931351244449615, 0.09893379360437393, 0.1251152902841568, 0.08649571985006332, 0.15260110795497894, 0.08412182331085205, 0.1277088075876236, 0.08932586759328842, 0.06589700281620026, 0.13841457664966583, 0.1029379740357399, 0.10102788358926773, 0.1150532141327858, 0.13943402469158173, 0.0714627131819725, 0.1646580994129181, 0.0990932285785675, 0.07059603929519653, 0.18626222014427185, 0.1527489870786667, 0.10483602434396744, 0.12513160705566406, 0.10733523219823837, 0.08152396976947784, 0.1319415271282196, 0.030792782083153725, 0.18744461238384247, 0.135304257273674, 0.15506508946418762, 0.11257124692201614, 0.13083042204380035, 0.11492061614990234, 0.1283058077096939, 0.12148119509220123, 0.13223493099212646, 0.16033935546875, 0.10678152740001678, 0.1498008668422699, 0.13504965603351593, 0.1701209545135498, 0.09495347738265991, 0.16883254051208496, 0.11209571361541748, 0.10274107754230499, 0.11581582576036453, 0.16735832393169403, 0.13778847455978394, 0.1593727320432663, 0.1385822296142578, 0.0506478026509285, 0.06329162418842316, 0.14981360733509064, 0.12323274463415146, 0.07824438810348511, 0.12423300743103027, 0.08180432766675949, 0.19614768028259277, 0.12110264599323273, 0.055937059223651886, 0.12662748992443085, 0.10242986679077148, 0.0843052864074707, 0.10723564028739929, 0.1416912078857422, 0.14069026708602905, 0.11469140648841858, 0.16604895889759064, 0.05980096757411957, 0.1207977682352066, 0.15296673774719238, 0.1626282036304474, 0.09646467864513397, 0.1850643903017044, 0.12292423099279404, 0.12496673315763474, 0.0325922854244709, 0.06783691793680191, 0.12160009145736694, 0.08238957077264786, 0.20158852636814117, 0.1899031400680542, 0.11379028856754303, 0.1468171626329422, 0.08930020779371262, 0.1354239284992218, 0.04235437139868736, 0.15115411579608917, 0.1436627060174942, 0.12959712743759155, 0.133011594414711, 0.11154019832611084, 0.0671946257352829, 0.04453784227371216, 0.17901365458965302, 0.07409682869911194, 0.076846644282341, 0.12521594762802124, 0.12394580245018005, 0.10956578701734543, 0.07196351140737534, 0.12697970867156982, 0.17157304286956787, 0.0802728533744812, 0.0837460309267044, 0.08677786588668823, 0.08424407988786697, 0.11412788927555084, 0.1621381789445877, 0.08773209154605865, 0.12338363379240036, 0.09298139065504074, 0.11278469115495682, 0.11548921465873718, 0.171061709523201, 0.13240152597427368, 0.128973126411438, 0.16890637576580048, 0.07577645778656006, 0.04861397668719292, 0.12741151452064514, 0.0668419599533081, 0.10878849029541016, 0.06823389232158661, 0.17077037692070007, 0.1801941990852356, 0.16926923394203186, 0.17389953136444092, 0.09879272431135178, 0.09556053578853607, 0.11188661307096481, 0.11475563049316406, 0.11339382082223892, 0.1384311318397522, 0.16153569519519806, 0.18949073553085327, 0.1299249231815338, 0.09725061058998108, 0.11247861385345459, 0.1498318314552307, 0.12587116658687592, 0.08677934110164642, 0.0806679055094719, 0.09934253245592117, 0.07857959717512131, 0.1947793960571289, 0.05685922130942345, 0.13553084433078766, 0.12687690556049347, 0.06602686643600464, 0.1519908607006073, 0.07385452091693878, 0.1486387997865677, 0.08206100016832352, 0.13016900420188904, 0.16337381303310394, 0.11452591419219971, 0.09052352607250214, 0.10218795388936996, 0.09148124605417252, 0.09689781069755554, 0.13670200109481812, 0.11101249605417252, 0.1212524026632309, 0.18875941634178162, 0.15614379942417145, 0.11341869086027145, 0.12961697578430176, 0.08592653274536133, 0.1580033153295517, 0.11331173032522202, 0.07884038984775543, 0.09774364531040192, 0.08613477647304535, 0.09706848859786987, 0.09615126997232437, 0.14348800480365753, 0.12966880202293396, 0.1439097821712494, 0.10582937300205231, 0.06478022783994675, 0.1056055873632431, 0.10637315362691879, 0.08148374408483505, 0.11362924426794052, 0.12456721812486649, 0.13033849000930786, 0.13984926044940948, 0.1099322959780693, 0.10880712419748306, 0.11690475046634674, 0.12707847356796265, 0.1366201490163803, 0.10562438517808914, 0.13800841569900513, 0.1063598245382309, 0.08983062207698822, 0.08700191974639893, 0.22178861498832703, 0.12959504127502441, 0.12001409381628036, 0.1671276092529297, 0.12453716993331909, 0.14033108949661255, 0.13187526166439056, 0.14714331924915314, 0.18552406132221222, 0.12607169151306152, 0.17552638053894043, 0.06677627563476562, 0.18179260194301605, 0.08470213413238525, 0.10894482582807541, 0.1289987415075302, 0.10088475793600082, 0.1612773835659027, 0.10865553468465805, 0.07763088494539261, 0.09173917770385742, 0.04653312265872955, 0.1836816817522049, 0.1273418366909027, 0.13174766302108765, 0.1062745451927185, 0.15673865377902985, 0.21758754551410675, 0.08321399241685867, 0.1693049520254135, 0.1193353608250618, 0.07640209794044495, 0.16128839552402496, 0.12720580399036407, 0.09846997261047363, 0.10121935606002808, 0.13000884652137756, 0.10416369885206223, 0.151520237326622, 0.0642443522810936, 0.1869686096906662, 0.17115864157676697, 0.08239669352769852, 0.09801214933395386, 0.19540055096149445, 0.14050941169261932, 0.1493636518716812, 0.1028866395354271, 0.1690537929534912, 0.11517433077096939, 0.08795198053121567, 0.12857377529144287, 0.18355174362659454, 0.08484979718923569, 0.1741926521062851, 0.12478849291801453, 0.8533687591552734, 0.8262100219726562, 0.9876620769500732, 0.733143150806427, 0.44916024804115295, 1.119172215461731, 0.9915031790733337, 0.2417469322681427, 0.9503103494644165, 1.1608543395996094, 1.2002538442611694, 0.9135636687278748, 1.0138353109359741, 0.5835757255554199, 0.4828314781188965, 0.4560799300670624, 0.6149647831916809, 1.0691580772399902, 0.6023094654083252, 1.2950313091278076, 0.7179972529411316, 1.120230793952942, 1.5309274196624756, 1.4247137308120728, 1.0472707748413086, 0.09398038685321808, 0.9370001554489136, 1.1556124687194824, 1.1236375570297241, 0.40763726830482483, 0.6054582595825195, 1.1162062883377075, 0.7359337210655212, 0.5656113028526306, 1.0442893505096436, 0.6560459136962891, 1.083376407623291, 0.6376972198486328, 0.8591750264167786, 0.8743156790733337, 0.9515349864959717, 0.8679008483886719, 0.9608425498008728, 0.8527007699012756, 0.8223488926887512, 0.777166485786438, 0.6590517163276672, 0.7703219652175903, 0.8977606892585754, 0.6348474621772766, 0.450154572725296, 1.2497916221618652, 1.2117536067962646, 0.6847184896469116, 0.6760215759277344, 0.43201300501823425, 0.8966488242149353, 0.7065470814704895, 0.7680400013923645, 0.547516942024231, 0.6682927012443542, 0.5299047231674194, 0.9082791805267334, 0.6423200964927673, 0.7946587800979614, 1.3941919803619385, 1.1453436613082886, 1.0462340116500854, 0.5368850827217102, 1.2341490983963013, 0.7880342602729797, 0.9437072277069092, 0.5546644330024719, 0.6087899804115295, 1.3505053520202637, 0.8459323048591614, 0.5002651810646057, 0.621902585029602, 0.6453809142112732, 0.8012159466743469, 0.42283499240875244, 0.4949077367782593, 0.8983743786811829, 0.5941044688224792, 1.3230397701263428, 1.3643792867660522, 1.322737693786621, 0.9633963704109192, 0.9140053987503052, 1.1637852191925049, 0.6121612787246704, 1.3344945907592773, 0.9436856508255005, 1.0670732259750366, 1.0279924869537354, 0.6441125273704529, 1.0276997089385986, 0.4245491027832031, 0.7154021263122559, 0.473300963640213, 0.4050535559654236, 0.9112808108329773, 1.4852508306503296, 0.8088381886482239, 0.8937740325927734, 0.5568525791168213, 0.9698813557624817, 1.294891119003296, 0.6157566905021667, 0.7079561352729797, 0.45574405789375305, 1.5826553106307983, 0.6781942844390869, 0.7699703574180603, 0.7008402943611145, 0.7902657389640808, 0.5003581643104553, 0.5555143356323242, 0.5034846663475037, 0.9993798136711121, 0.5596060752868652, 1.3386080265045166, 0.6310845613479614, 0.9126781821250916, 0.8222500681877136, 0.46653637290000916, 0.6475996971130371, 0.9577824473381042, 1.2357804775238037, 0.8442919850349426, 0.41528716683387756, 1.4057095050811768, 0.7652155160903931, 0.8740692138671875, 1.0565714836120605, 0.8008381724357605, 0.5412759780883789, 1.1814281940460205, 0.9210165143013, 1.070812463760376, 0.5783672332763672, 0.6262400150299072, 1.1300227642059326, 0.8461576700210571, 0.9820327758789062, 1.1046209335327148, 0.5805577039718628, 0.6932937502861023, 0.8023426532745361, 0.856523334980011, 1.0233330726623535, 1.4985618591308594, 0.7502339482307434, 1.0059152841567993, 0.6161248087882996, 1.3851535320281982, 0.8198387026786804, 1.281996726989746, 0.6813540458679199, 1.3027081489562988, 0.8878109455108643, 0.9964260458946228, 0.9766284227371216, 0.7777047753334045, 0.7367920279502869, 0.865118682384491, 0.28940367698669434, 0.7748936414718628, 0.7508109211921692, 0.9684261679649353, 0.9303576350212097, 1.0603771209716797, 0.6267964243888855, 0.4095132350921631, 0.8973580598831177, 0.9111807942390442, 0.5202651619911194, 0.5723451972007751, 0.5559450387954712, 1.1309058666229248, 1.363337516784668, 1.0276713371276855, 0.6978196501731873, 0.5322902202606201, 0.503130316734314, 0.9852892756462097, 1.2215533256530762, 0.9187119603157043, 1.1507949829101562, 1.058239459991455, 1.6307270526885986, 1.322316288948059, 0.49658092856407166, 0.6826777458190918, 0.8984328508377075, 1.1356356143951416, 1.2035763263702393, 1.2048912048339844, 0.6288884878158569, 0.8262138366699219, 1.3434274196624756, 0.9328864216804504, 1.2907421588897705, 0.7728751301765442, 1.4286248683929443, 0.42516666650772095, 0.4821009635925293, 0.5969008207321167, 1.0501166582107544, 0.6649172902107239, 0.8901352286338806, 0.4721963405609131, 0.6753568649291992, 1.4870420694351196, 1.1110224723815918, 0.8234468698501587, 0.8783389329910278, 0.6625486612319946, 1.2977705001831055, 0.8758480548858643, 0.5635882616043091, 0.6017834544181824, 0.5869393944740295, 0.6946398019790649, 1.2072093486785889, 0.5269306302070618, 1.517869234085083, 0.753018856048584, 1.0394659042358398, 1.0840754508972168, 0.5335468649864197, 1.1949121952056885, 0.6873513460159302, 0.9139132499694824, 1.4774340391159058, 1.1245942115783691, 0.9915367960929871, 1.4247773885726929, 0.8272602558135986, 0.6559040546417236, 1.0659515857696533, 0.7530377507209778, 0.8347904682159424, 1.3191522359848022, 0.7060958743095398, 0.8447669744491577, 1.1887669563293457, 1.1085089445114136, 0.4109174907207489, 0.9383719563484192, 0.6624906659126282, 0.7929728627204895, 0.5469868183135986, 0.9774311780929565, 0.5505813360214233, 1.1367841958999634, 0.8450425267219543, 0.8803436160087585, 1.1678218841552734, 0.6740350127220154, 0.7121468782424927, 0.5104983448982239, 0.700669527053833, 1.07323157787323, 1.0921415090560913, 0.646452784538269, 0.8350955247879028, 1.1181062459945679, 1.1999002695083618, 0.7861078381538391, 0.9708011150360107, 0.8668870329856873, 0.8502995371818542, 0.895030677318573, 0.8550847172737122, 0.47071585059165955, 0.8300085067749023, 0.6722652912139893, 1.0044214725494385, 0.7438777089118958, 0.8013534545898438, 0.6450962424278259, 0.9467121958732605, 0.7416963577270508, 1.0912151336669922, 0.6181934475898743, 0.8830178380012512, 0.9162566661834717, 0.7511046528816223, 0.7231060862541199, 0.9827849864959717, 1.123396396636963, 0.8877221345901489, 0.4610167145729065, 1.4862807989120483, 0.9169848561286926, 1.01069176197052, 0.9395976066589355, 0.3977191746234894, 0.7931718230247498, 41.27655029296875, 97.6962890625, 49.972900390625, 118.72563934326172, 71.01454162597656, 21.310123443603516, 82.26908111572266, 29.11087417602539, 54.0421142578125, 15.19677734375, 25.433866500854492, 34.50543975830078, 16.95035171508789, 64.09173583984375, 45.4537239074707, 75.85503387451172, 157.93231201171875, 133.96575927734375, 188.6695098876953, 60.10776138305664, 40.10002136230469, 99.5999755859375, 50.9036865234375, 49.3583984375, 105.35509490966797, 54.699501037597656, 79.12554168701172, 35.72528076171875, 73.23294067382812, 65.51811981201172, 178.7137908935547, 31.801881790161133, 31.686370849609375, 59.75161361694336, 32.49782943725586, 22.81318473815918, 81.5802001953125, 68.3779067993164, 176.15576171875, 56.45583724975586, 80.17742919921875, 19.03458023071289, 58.44773483276367, 164.3095245361328, 76.337890625, 42.624603271484375, 37.98691177368164, 23.880998611450195, 101.51280212402344, 104.89659881591797, 50.233489990234375, 37.29228591918945, 16.936248779296875, 24.35919189453125, 199.05914306640625, 18.703109741210938, 77.34058380126953, 35.84103012084961, 19.56658935546875, 62.63714599609375, 15.110321044921875, 210.74053955078125, 12.962127685546875, 42.356658935546875, 61.612186431884766, 118.65189361572266, 45.56471633911133, 50.32588577270508, 56.964149475097656, 60.38849639892578, 21.11041259765625, 28.858497619628906, 27.58228874206543, 150.23175048828125, 35.2247314453125, 28.026214599609375, 80.02677154541016, 74.66029357910156, 26.59820556640625, 39.90171432495117, 66.9025650024414, 50.884521484375, 31.910741806030273, 27.303466796875, 27.41694450378418, 21.15826416015625, 39.90496826171875, 109.0780029296875, 37.38720703125, 70.73846435546875, 279.48309326171875, 34.20571517944336, 167.96311950683594, 27.176044464111328, 72.37130737304688, 29.00101089477539, 111.77972412109375, 39.662445068359375, 22.645904541015625, 54.500732421875, 39.209930419921875, 138.81668090820312, 25.89642333984375, 22.37782096862793, 30.213226318359375, 118.0185546875, 156.82376098632812, 44.7752685546875, 66.35527801513672, 82.1670913696289, 13.9050874710083, 71.89588165283203, 27.64264678955078, 59.67707061767578, 62.758460998535156, 76.55245208740234, 33.589202880859375, 83.04448699951172, 17.62493896484375, 56.98561477661133, 20.605873107910156, 51.050048828125, 91.45362091064453, 58.86050796508789, 36.61524963378906, 103.41220092773438, 23.4454345703125, 22.255661010742188, 85.12041473388672, 64.49878692626953, 86.42916107177734, 73.68709564208984, 80.93238830566406, 84.45233154296875, 72.14984130859375, 28.34967041015625, 72.66905975341797, 54.306697845458984, 20.895170211791992, 44.53359603881836, 104.54593658447266, 51.34639358520508, 98.40911865234375, 16.471359252929688, 114.96953582763672, 23.141483306884766, 51.63332748413086, 125.49433135986328, 29.208036422729492, 166.39013671875, 221.4065704345703, 107.16598510742188, 21.79541015625, 104.24330139160156, 42.06072235107422, 21.721481323242188, 23.613037109375, 149.1320037841797, 21.714345932006836, 104.9285888671875, 61.963523864746094, 78.05703735351562, 164.76272583007812, 33.69558334350586, 48.35318374633789, 11.416778564453125, 220.7913818359375, 22.26092529296875, 24.712318420410156, 44.2486572265625, 33.05047607421875, 91.44170379638672, 133.48245239257812, 36.652801513671875, 74.3229751586914, 52.624114990234375, 109.33390045166016, 14.15582275390625, 42.093807220458984, 41.2200813293457, 106.260498046875, 51.94790267944336, 64.70816802978516, 51.09124755859375, 68.96234130859375, 52.67463684082031, 81.37605285644531, 30.26026725769043, 73.91452026367188, 19.3441162109375, 73.53799438476562, 39.78364181518555, 42.08243942260742, 80.98056030273438, 56.99949264526367, 124.81136322021484, 47.11572265625, 64.29044342041016, 72.03849029541016, 46.43403625488281, 79.40425872802734, 55.95288848876953, 102.72588348388672, 26.259544372558594, 51.83685302734375, 34.9952392578125, 64.69721221923828, 35.19350814819336, 72.4339599609375, 19.764190673828125, 77.72905731201172, 107.80542755126953, 34.46347427368164, 22.688383102416992, 18.550052642822266, 35.05055236816406, 67.18826293945312, 17.8331298828125, 41.607666015625, 65.12435913085938, 39.69775390625, 17.827329635620117, 22.836793899536133, 58.02993392944336, 110.0448989868164, 123.096435546875, 23.144775390625, 41.56892395019531, 64.00946044921875, 33.16021728515625, 25.52117919921875, 22.629318237304688, 32.5911865234375, 53.93408966064453, 115.28409576416016, 23.118133544921875, 52.9814453125, 22.568422317504883, 66.05522155761719, 75.33523559570312, 76.59469604492188, 72.53720092773438, 64.6263427734375, 72.83856964111328, 84.11070251464844, 85.0712661743164, 75.76763153076172, 20.106903076171875, 15.202056884765625, 48.00068283081055, 32.70705795288086, 25.807601928710938, 43.88756561279297, 20.540239334106445, 48.79773712158203, 50.084285736083984, 55.37502670288086, 16.350526809692383, 55.43418884277344, 69.0123291015625, 18.77463150024414, 131.8139190673828, 38.27199935913086, 59.85181427001953, 30.18585205078125, 43.233123779296875, 107.644775390625, 17.8907470703125, 140.98475646972656, 22.78322410583496, 38.13247299194336, 53.1988525390625, 111.24050903320312, 55.194305419921875, 27.32927703857422, 33.05546188354492, 34.877777099609375, 55.37514877319336, 67.74481201171875, 33.4979248046875, 23.931686401367188, 33.04444885253906, 83.12085723876953, 95.27804565429688, 48.5833625793457, 35.521270751953125, 148.1464080810547, 39.491493225097656, 22.440996170043945, 45.22316360473633, 154.61746215820312, 58.530609130859375, 37.7972412109375, 47.82025146484375, 42.11281967163086, 138.25762939453125, 55.68276596069336, 131.00601196289062, 32.048980712890625, 38.86322021484375, 2.016240119934082, 2.321084499359131, 2.9042916297912598, 1.9760093688964844, 1.8084430694580078, 2.8995440006256104, 2.0701019763946533, 2.9155566692352295, 2.6325628757476807, 3.6329433917999268, 2.482745409011841, 2.2724409103393555, 2.2374277114868164, 2.000507354736328, 1.4251073598861694, 1.6581792831420898, 2.081702470779419, 3.0265421867370605, 2.6883232593536377, 2.8629448413848877, 2.6413683891296387, 1.170332908630371, 2.152113199234009, 0.9792578816413879, 1.0989793539047241, 2.381234645843506, 2.8693859577178955, 2.4423913955688477, 1.8013566732406616, 1.3397163152694702, 1.2952358722686768, 2.6623470783233643, 2.483142137527466, 2.44930362701416, 2.4346437454223633, 2.1805758476257324, 2.415851354598999, 2.377924919128418, 3.060577869415283, 2.1513404846191406, 2.1721792221069336, 1.89696204662323, 1.877327799797058, 1.9067227840423584, 2.0458898544311523, 1.6146823167800903, 2.0478124618530273, 3.5056984424591064, 2.366328001022339, 2.213973045349121, 2.3283071517944336, 3.3755903244018555, 2.506931781768799, 2.798781156539917, 3.379868745803833, 2.135220527648926, 2.114471912384033, 1.7739651203155518, 2.501408576965332, 2.7723824977874756, 1.8742727041244507, 2.6356048583984375, 1.985526204109192, 2.9484832286834717, 2.925278902053833, 1.7751836776733398, 2.2613601684570312, 2.3307621479034424, 3.055670738220215, 2.598264217376709, 2.2712831497192383, 2.5357351303100586, 1.8845739364624023, 3.1078460216522217, 3.06036114692688, 1.9023230075836182, 2.2371625900268555, 1.9728317260742188, 1.5859627723693848, 2.449164867401123, 1.5700674057006836, 1.65074622631073, 1.0100144147872925, 1.9607343673706055, 2.121819496154785, 3.0756945610046387, 1.8883473873138428, 1.974471092224121, 2.2118959426879883, 2.0977678298950195, 1.9321411848068237, 2.081676959991455, 2.7845277786254883, 2.735621213912964, 2.056934356689453, 1.7991760969161987, 1.5070523023605347, 3.0696449279785156, 2.0133166313171387, 3.143267869949341, 1.6826128959655762, 3.272367477416992, 3.060614824295044, 2.3471784591674805, 1.5543584823608398, 2.144258737564087, 2.3808300495147705, 2.946976900100708, 2.5191409587860107, 3.5660240650177, 2.9435417652130127, 1.3387197256088257, 1.8031949996948242, 2.3243303298950195, 1.9371709823608398, 1.1097021102905273, 3.057746171951294, 2.29449462890625, 1.91102135181427, 2.857449769973755, 3.0450775623321533, 2.90336537361145, 1.8664236068725586, 1.5914154052734375, 2.0759401321411133, 1.8429059982299805, 2.2994511127471924, 3.3200368881225586, 2.9022858142852783, 2.3160955905914307, 1.5730942487716675, 2.2509639263153076, 1.9373977184295654, 2.8539230823516846, 2.4462366104125977, 2.550175666809082, 1.5572210550308228, 3.295766592025757, 3.1649982929229736, 2.036564826965332, 1.9877386093139648, 1.7917001247406006, 1.7823705673217773, 1.7832423448562622, 2.1873064041137695, 3.0778889656066895, 2.207639694213867, 2.436969518661499, 1.183674693107605, 3.2132656574249268, 2.2030868530273438, 2.7966949939727783, 1.5639448165893555, 1.6793889999389648, 3.427043914794922, 2.0363245010375977, 2.45230770111084, 2.1388559341430664, 1.81246817111969, 2.038417100906372, 2.74552059173584, 2.48836088180542, 2.7732739448547363, 1.7270793914794922, 1.9937245845794678, 2.37404465675354, 2.041632652282715, 2.0255861282348633, 1.7910330295562744, 1.8301360607147217, 1.4988110065460205, 2.2638661861419678, 1.5386861562728882, 2.5539238452911377, 1.96358060836792, 2.637958288192749, 1.2182130813598633, 2.8998184204101562, 1.9033976793289185, 2.1243040561676025, 3.0793297290802, 2.2781496047973633, 1.3246392011642456, 1.4546173810958862, 3.1797637939453125, 1.9147628545761108, 2.121068000793457, 1.6324970722198486, 2.132845878601074, 2.5166475772857666, 1.7846726179122925, 1.7116001844406128, 3.7661046981811523, 3.087477445602417, 1.6168928146362305, 1.8290804624557495, 2.801717758178711, 3.632589101791382, 2.333035469055176, 3.085986375808716, 3.1173930168151855, 2.2533979415893555, 3.214789390563965, 3.543903112411499, 2.7438855171203613, 2.0943641662597656, 1.8465272188186646, 1.8532456159591675, 2.5693676471710205, 3.0444555282592773, 1.183241844177246, 3.1540896892547607, 2.200312614440918, 2.7075908184051514, 1.7787717580795288, 1.4650421142578125, 2.4338502883911133, 1.7682305574417114, 2.7972137928009033, 1.738633632659912, 1.863930583000183, 3.2909977436065674, 1.0759916305541992, 1.4329328536987305, 2.3469481468200684, 1.7514758110046387, 2.7659547328948975, 2.5649654865264893, 1.9535950422286987, 1.5328394174575806, 1.7599148750305176, 3.4083127975463867, 1.6598178148269653, 2.6123979091644287, 1.6884936094284058, 2.5218019485473633, 1.9863845109939575, 2.8945839405059814, 3.1830685138702393, 1.5842162370681763, 2.027420997619629, 2.793919086456299, 2.769183397293091, 1.6639162302017212, 2.3733205795288086, 2.0623044967651367, 1.368949055671692, 1.7590454816818237, 2.7100024223327637, 2.746230363845825, 2.639420986175537, 2.393416404724121, 1.3237621784210205, 1.9739632606506348, 1.2273989915847778, 3.013676643371582, 1.4681453704833984, 1.6258591413497925, 2.0205307006835938, 2.601973295211792, 2.640631914138794, 2.6972644329071045, 3.212355375289917, 1.7625617980957031, 1.8597573041915894, 3.1811625957489014, 3.254000663757324, 1.3012176752090454, 2.4555559158325195, 2.4476726055145264, 2.0838463306427, 2.3812103271484375, 2.4177746772766113, 2.940760850906372, 2.639380931854248, 1.9658946990966797, 2.099102735519409, 1.8266963958740234, 1.9026139974594116, 2.3504021167755127, 2.385432004928589, 3.0340607166290283, 2.0052640438079834, 2.7302966117858887, 2.4504988193511963, 2.0037012100219727, 2.665273427963257, 1.7998380661010742, 1.5758047103881836, 3.358039140701294, 1.8040812015533447, 1.2505292892456055, 1.6202600002288818, 1.7398196458816528, 1.9524813890457153, 2.1193017959594727, 2.58530330657959, 1.6321932077407837, 2.0043187141418457, 2.859365224838257, 0.12011092901229858, 0.1124425083398819, 0.12586630880832672, 0.12839627265930176, 0.1289171278476715, 0.0902872234582901, 0.12128811329603195, 0.06714460253715515, 0.1440923810005188, 0.12988775968551636, 0.12998338043689728, 0.0446939542889595, 0.12939004600048065, 0.033808741718530655, 0.13496330380439758, 0.0780661404132843, 0.12931062281131744, 0.09003656357526779, 0.19374120235443115, 0.09359976649284363, 0.11097650229930878, 0.14811433851718903, 0.16521725058555603, 0.16085010766983032, 0.10232024639844894, 0.13205371797084808, 0.07339641451835632, 0.0961986556649208, 0.12361465394496918, 0.11008107662200928, 0.09640388935804367, 0.14750903844833374, 0.14401735365390778, 0.1167106032371521, 0.10387822985649109, 0.1526828408241272, 0.15981420874595642, 0.14896737039089203, 0.25016406178474426, 0.11118093132972717, 0.13308776915073395, 0.11056087166070938, 0.14122004806995392, 0.12040942907333374, 0.21465209126472473, 0.11245084553956985, 0.120090551674366, 0.16596561670303345, 0.14353299140930176, 0.1723601520061493, 0.11766576766967773, 0.12399227172136307, 0.10959330201148987, 0.12753675878047943, 0.13163961470127106, 0.11087989807128906, 0.09164956957101822, 0.11760371923446655, 0.14474032819271088, 0.16486619412899017, 0.07243955135345459, 0.0784992128610611, 0.16460220515727997, 0.13738399744033813, 0.09943637996912003, 0.17383018136024475, 0.10009954124689102, 0.14331218600273132, 0.11836477369070053, 0.12303520739078522, 0.1018807515501976, 0.1857692152261734, 0.09158417582511902, 0.11868494004011154, 0.1363557130098343, 0.040474481880664825, 0.13791479170322418, 0.2055835723876953, 0.09472745656967163, 0.1045239046216011, 0.13711193203926086, 0.13794471323490143, 0.13081558048725128, 0.12482117116451263, 0.0700569674372673, 0.13423070311546326, 0.08780107647180557, 0.17618799209594727, 0.20367412269115448, 0.15808601677417755, 0.13929836452007294, 0.1843532770872116, 0.1771078109741211, 0.07641929388046265, 0.12992656230926514, 0.09048019349575043, 0.1091475561261177, 0.10487174987792969, 0.169338658452034, 0.13929153978824615, 0.11285658925771713, 0.19470088183879852, 0.1736011803150177, 0.12014750391244888, 0.07301273941993713, 0.0923825055360794, 0.12546098232269287, 0.06688147038221359, 0.0640578642487526, 0.11939729750156403, 0.19140774011611938, 0.12195372581481934, 0.10413023829460144, 0.12890101969242096, 0.136826753616333, 0.14696606993675232, 0.16651593148708344, 0.11196308583021164, 0.08695663511753082, 0.21324634552001953, 0.1259281188249588, 0.14151370525360107, 0.11112415790557861, 0.09045028686523438, 0.09577172994613647, 0.11653470993041992, 0.15705157816410065, 0.12511968612670898, 0.11988761276006699, 0.20725516974925995, 0.10895783454179764, 0.0422208197414875, 0.13830804824829102, 0.09460926055908203, 0.16452641785144806, 0.12261795997619629, 0.13601195812225342, 0.08120273053646088, 0.06358776241540909, 0.17873232066631317, 0.09552150219678879, 0.15335562825202942, 0.12207722663879395, 0.16039340198040009, 0.1303989142179489, 0.16738486289978027, 0.17042218148708344, 0.10461902618408203, 0.12046991288661957, 0.11514521390199661, 0.11214011907577515, 0.09628041088581085, 0.14103452861309052, 0.10868358612060547, 0.09734414517879486, 0.1033514067530632, 0.11219840496778488, 0.169743612408638, 0.12684234976768494, 0.1440630555152893, 0.2118503898382187, 0.11267994344234467, 0.14875708520412445, 0.10439395904541016, 0.14424487948417664, 0.06954052299261093, 0.1339094340801239, 0.18723373115062714, 0.05012553930282593, 0.13238801062107086, 0.1453496366739273, 0.12238955497741699, 0.108192078769207, 0.14192086458206177, 0.08914341032505035, 0.16077540814876556, 0.13216149806976318, 0.21469171345233917, 0.1693006455898285, 0.11202012747526169, 0.10710019618272781, 0.17704732716083527, 0.14095474779605865, 0.11420690268278122, 0.07175219058990479, 0.05598112568259239, 0.13974148035049438, 0.0703510046005249, 0.1077975407242775, 0.11391953378915787, 0.04166007041931152, 0.23717784881591797, 0.12824876606464386, 0.10809173434972763, 0.17724204063415527, 0.12848854064941406, 0.1457929015159607, 0.14518462121486664, 0.08759302645921707, 0.15723413228988647, 0.12180779874324799, 0.10777422040700912, 0.102078877389431, 0.07548762857913971, 0.1421590894460678, 0.22721564769744873, 0.13552933931350708, 0.11824966222047806, 0.10595013201236725, 0.15070973336696625, 0.109415203332901, 0.10919725894927979, 0.2199263572692871, 0.21455012261867523, 0.14705629646778107, 0.09498944878578186, 0.09827818721532822, 0.08573976159095764, 0.12859715521335602, 0.14147581160068512, 0.16482478380203247, 0.1637011617422104, 0.09196043014526367, 0.08630956709384918, 0.09811113029718399, 0.22326095402240753, 0.11518330127000809, 0.1558019071817398, 0.16320255398750305, 0.13074778020381927, 0.14779624342918396, 0.17464414238929749, 0.11072506010532379, 0.16141287982463837, 0.16975274682044983, 0.1711195409297943, 0.08181135356426239, 0.10791432857513428, 0.1986897587776184, 0.11971263587474823, 0.20651982724666595, 0.08909887075424194, 0.14701223373413086, 0.11428909748792648, 0.09587237983942032, 0.08286178112030029, 0.13942408561706543, 0.113245390355587, 0.102381132543087, 0.09460769593715668, 0.08719996362924576, 0.10220801830291748, 0.1894388496875763, 0.1081354022026062, 0.09037818759679794, 0.16315892338752747, 0.12971141934394836, 0.16459716856479645, 0.062002312391996384, 0.11756593734025955, 0.14621369540691376, 0.1581183224916458, 0.1866946518421173, 0.04029560461640358, 0.12655121088027954, 0.16972602903842926, 0.16740812361240387, 0.09917549788951874, 0.15887948870658875, 0.0722687765955925, 0.1314990520477295, 0.18639980256557465, 0.16608493030071259, 0.10410201549530029, 0.18376101553440094, 0.09625764936208725, 0.08198153227567673, 0.11592545360326767, 0.11504242569208145, 0.16788451373577118, 0.1610802412033081, 0.13459773361682892, 0.1021651029586792, 0.10389658808708191, 0.0724300667643547, 0.10637194663286209, 0.15230786800384521, 0.12922467291355133, 0.1308194100856781, 0.07906409353017807, 0.2466442883014679, 0.11336648464202881, 0.1283894032239914, 0.11291387677192688, 0.05928534269332886, 0.08807023614645004, 0.05274419113993645, 0.11237066984176636, 0.0902242437005043, 0.11992406845092773, 0.7575778961181641, 0.3523365557193756, 1.0661535263061523, 1.4676522016525269, 1.0125399827957153, 0.6947795748710632, 1.0833278894424438, 1.011509656906128, 0.8418738842010498, 0.7358380556106567, 0.5850688219070435, 0.5973219275474548, 1.068308711051941, 0.9818539023399353, 0.351357102394104, 0.7906592488288879, 1.5902519226074219, 1.503363013267517, 0.7879989743232727, 1.1498123407363892, 0.955768883228302, 1.0916889905929565, 1.1467589139938354, 0.7286378145217896, 1.0360360145568848, 0.8218262791633606, 0.6994147300720215, 0.8072145581245422, 1.2506576776504517, 1.0874013900756836, 0.5433731079101562, 0.8859591484069824, 0.6961466073989868, 1.1472363471984863, 0.6906812787055969, 0.9992810487747192, 0.6486114859580994, 0.6045613884925842, 1.157104730606079, 0.8139931559562683, 0.5296664237976074, 1.0034451484680176, 0.9764352440834045, 1.041954517364502, 0.6747363209724426, 1.0891356468200684, 1.410498023033142, 1.4299463033676147, 0.5849880576133728, 1.0979769229888916, 0.6000994443893433, 0.9977038502693176, 1.049483299255371, 0.49985775351524353, 0.9985114932060242, 1.1054632663726807, 0.689736545085907, 0.6885101199150085, 0.6810916066169739, 0.8693603873252869, 0.9582436680793762, 0.9706255197525024, 0.9374502301216125, 0.9881767630577087, 0.9367550611495972, 0.7475881576538086, 0.6658816337585449, 0.48521003127098083, 1.1700588464736938, 0.8389399647712708, 1.265785813331604, 0.7735036015510559, 0.8191397786140442, 0.6934128403663635, 0.7113279700279236, 0.5403560996055603, 0.7120625376701355, 1.1187154054641724, 0.5405493974685669, 0.6672584414482117, 0.864339292049408, 0.568571925163269, 1.1835691928863525, 0.8215625286102295, 0.8146169781684875, 0.7236388325691223, 0.7318794131278992, 0.8627831339836121, 0.7076190114021301, 0.6274576783180237, 0.5758727788925171, 0.5978976488113403, 0.841480553150177, 0.8321707844734192, 1.4068033695220947, 1.2150747776031494, 0.9118847250938416, 0.7358586192131042, 0.6841172575950623, 1.370328664779663, 0.460018515586853, 0.5905435085296631, 0.6778775453567505, 0.6321289539337158, 0.8542751669883728, 0.9468534588813782, 0.40103498101234436, 0.6693865060806274, 0.8375876545906067, 0.6440478563308716, 0.8033329844474792, 1.1871644258499146, 1.1050013303756714, 1.2222063541412354, 1.1037157773971558, 1.2318719625473022, 0.936511218547821, 1.1749300956726074, 1.2795227766036987, 0.9238665699958801, 1.0731064081192017, 0.9388461112976074, 0.9567060470581055, 1.193603515625, 1.2978274822235107, 0.7568886876106262, 0.516200602054596, 1.5487568378448486, 0.4943391978740692, 0.8851640224456787, 0.5112171173095703, 0.9042941331863403, 1.05660080909729, 0.95925372838974, 0.8331311345100403, 0.7986854314804077, 1.2441320419311523, 0.685656726360321, 1.1947675943374634, 0.5833820700645447, 1.5130681991577148, 0.7859992980957031, 0.8436709642410278, 0.9288146495819092, 0.5671027898788452, 0.5436702370643616, 0.5134060382843018, 0.8337727785110474, 0.6482083201408386, 0.8792586326599121, 1.2103397846221924, 0.9701481461524963, 1.0356221199035645, 1.841377854347229, 0.6399314999580383, 1.3894541263580322, 0.803821861743927, 0.5868008136749268, 1.2409436702728271, 0.8233299255371094, 1.0384937524795532, 0.585636556148529, 0.6421502828598022, 0.7758772969245911, 0.9717958569526672, 0.8245542645454407, 0.9377506971359253, 1.2364014387130737, 0.9650138020515442, 1.1355230808258057, 0.7844794988632202, 0.885802149772644, 1.1882386207580566, 1.113808274269104, 1.3538885116577148, 0.75385582447052, 0.7662128806114197, 1.063866376876831, 0.6134662628173828, 1.1555073261260986, 0.8508852124214172, 0.7884133458137512, 1.0352535247802734, 0.6926555633544922, 0.6608021259307861, 0.44579359889030457, 0.7404974102973938, 1.2941043376922607, 0.7277520298957825, 0.7582476735115051, 0.7640547156333923, 0.776739239692688, 1.754598617553711, 1.299963355064392, 1.197440505027771, 0.7285739183425903, 0.6912501454353333, 0.5259780883789062, 0.8229702711105347, 0.6684263348579407, 0.6109680533409119, 1.3980451822280884, 0.5219104886054993, 1.074263095855713, 0.9247798919677734, 1.2368026971817017, 0.9911823272705078, 0.8177846074104309, 0.4737081527709961, 1.2912349700927734, 0.6353406310081482, 1.4214190244674683, 1.1280230283737183, 1.1578028202056885, 0.7329937815666199, 0.6989574432373047, 0.46161994338035583, 1.0745995044708252, 0.47149214148521423, 0.939520001411438, 1.3871341943740845, 1.1041722297668457, 1.189064621925354, 0.6341705322265625, 0.6945798993110657, 0.762934684753418, 0.3380700647830963, 1.0099101066589355, 1.3359777927398682, 0.5870555639266968, 1.106339931488037, 0.5085071921348572, 1.2035236358642578, 0.5533671975135803, 0.6966153383255005, 0.667776346206665, 1.2904348373413086, 1.8389147520065308, 0.7296155095100403, 1.2347626686096191, 1.0042928457260132, 0.49141883850097656, 0.9049223065376282, 1.4273681640625, 0.8740516304969788, 0.869564950466156, 0.6025612354278564, 0.9220712780952454, 1.8831968307495117, 0.9099071025848389, 1.14452064037323, 0.8152134418487549, 0.5991733074188232, 0.9613377451896667, 0.6664159893989563, 1.1226040124893188, 0.6709274649620056, 0.8978500366210938, 0.46904653310775757, 0.5312942862510681, 1.0107331275939941, 1.282617211341858, 1.0023064613342285, 0.5525280833244324, 1.0802407264709473, 0.48561975359916687, 0.9197292327880859, 0.5886196494102478, 0.5252273678779602, 1.008058786392212, 1.137678861618042, 1.296777367591858, 0.31365522742271423, 0.47584840655326843, 0.333672434091568, 0.7976288199424744, 1.0204306840896606, 0.49660491943359375, 0.771655797958374, 0.6583017110824585, 0.8674131631851196, 1.4549763202667236, 1.1857670545578003, 0.971942126750946, 0.4439104497432709, 1.3000015020370483, 0.756575882434845, 1.1795628070831299, 0.906848132610321, 1.0110723972320557, 1.032991647720337, 1.1878736019134521, 0.7210143208503723, 0.5203899145126343, 1.155032992362976, 0.5485799312591553, 1.232850193977356, 0.8831406831741333, 1.0992063283920288, 1.1168838739395142, 37.19409942626953, 102.04228973388672, 15.726226806640625, 60.389373779296875, 146.82232666015625, 22.83575439453125, 29.02300453186035, 52.82080078125, 31.149139404296875, 31.06903648376465, 45.950286865234375, 22.91314697265625, 20.860876083374023, 73.24673461914062, 24.29290771484375, 31.94207763671875, 20.546661376953125, 20.933685302734375, 111.10682678222656, 63.1148681640625, 155.217041015625, 19.04678726196289, 22.489990234375, 72.5929946899414, 43.11524200439453, 67.2601318359375, 85.66487121582031, 113.7193832397461, 86.48790740966797, 86.5020523071289, 19.17205810546875, 80.22395324707031, 21.388402938842773, 67.54244995117188, 147.34283447265625, 23.23284912109375, 39.71674728393555, 82.394287109375, 102.3313980102539, 166.8537139892578, 75.46766662597656, 16.041175842285156, 21.680044174194336, 98.38308715820312, 20.36994171142578, 50.0654296875, 165.33457946777344, 53.645076751708984, 117.85575103759766, 21.673030853271484, 50.763221740722656, 104.41725158691406, 40.48658752441406, 115.38992309570312, 105.05340576171875, 18.00531005859375, 56.72231674194336, 136.9320831298828, 48.19549560546875, 85.53306579589844, 33.44193649291992, 19.740203857421875, 45.876434326171875, 111.07708740234375, 44.664310455322266, 21.618680953979492, 66.09451293945312, 47.17645263671875, 52.896728515625, 78.25628662109375, 18.262054443359375, 20.810834884643555, 20.63736343383789, 50.62709045410156, 98.78884887695312, 84.10330963134766, 49.223480224609375, 96.124755859375, 37.946380615234375, 112.21280670166016, 70.80469512939453, 19.996755599975586, 21.461650848388672, 38.817203521728516, 12.031768798828125, 19.099700927734375, 24.0281982421875, 30.64801025390625, 74.93071746826172, 36.45686340332031, 19.027477264404297, 58.8326416015625, 50.01841354370117, 70.63516235351562, 15.994843482971191, 44.38894271850586, 41.72412872314453, 62.17751693725586, 22.385969161987305, 219.02862548828125, 17.99067497253418, 130.45892333984375, 152.27633666992188, 47.852783203125, 81.607666015625, 122.35851287841797, 107.27874755859375, 143.04417419433594, 21.593088150024414, 28.376976013183594, 51.412200927734375, 73.39884948730469, 102.23878479003906, 138.64712524414062, 33.34503173828125, 259.3157958984375, 21.421293258666992, 61.14738082885742, 40.11855697631836, 23.206512451171875, 16.46148681640625, 33.99143981933594, 74.50062561035156, 40.93259811401367, 133.09194946289062, 175.06468200683594, 45.71868896484375, 77.88717651367188, 80.25799560546875, 72.08544921875, 23.63547706604004, 52.0223388671875, 38.31689453125, 98.06285095214844, 54.68330001831055, 53.52590560913086, 39.28753662109375, 49.64826965332031, 18.189788818359375, 72.50540161132812, 141.8498077392578, 26.860057830810547, 125.76742553710938, 73.06201934814453, 96.8030776977539, 64.76254272460938, 143.9684600830078, 84.29293060302734, 85.56655883789062, 102.408935546875, 47.30363082885742, 179.57583618164062, 41.27818298339844, 60.14567565917969, 179.66964721679688, 84.63009643554688, 81.03741455078125, 32.49722671508789, 72.79808807373047, 25.7039794921875, 48.89780044555664, 64.66057586669922, 101.956298828125, 31.769622802734375, 84.76810455322266, 25.1517333984375, 25.3531494140625, 24.612762451171875, 34.810874938964844, 41.72490310668945, 76.22774505615234, 17.40266227722168, 95.41517639160156, 129.8168487548828, 42.92433547973633, 42.89124298095703, 39.431480407714844, 54.464691162109375, 27.44703483581543, 28.71103858947754, 81.62197875976562, 61.854248046875, 71.82852172851562, 103.34066009521484, 63.66351318359375, 46.60826110839844, 83.95323944091797, 56.372283935546875, 120.99868774414062, 76.61431121826172, 106.8778076171875, 45.455078125, 25.312734603881836, 28.316650390625, 82.40998077392578, 88.08650970458984, 47.789886474609375, 100.2367935180664, 131.91671752929688, 88.47964477539062, 23.70098876953125, 18.455018997192383, 42.878753662109375, 36.296600341796875, 37.19195556640625, 19.056859970092773, 112.96607971191406, 65.34951782226562, 78.44245147705078, 28.49322509765625, 67.11932373046875, 37.16253662109375, 89.96309661865234, 63.40980911254883, 50.46064376831055, 107.96951293945312, 55.99428939819336, 66.88589477539062, 60.74017333984375, 116.5062484741211, 86.83747863769531, 36.13713073730469, 90.82437896728516, 57.47552490234375, 148.2935333251953, 51.14936447143555, 34.127689361572266, 43.51887512207031, 88.71617126464844, 85.926025390625, 74.00215148925781, 51.08681106567383, 92.3393325805664, 84.44744873046875, 20.32806396484375, 27.330692291259766, 19.81561279296875, 40.01956558227539, 82.38115692138672, 23.275970458984375, 36.234134674072266, 111.09913635253906, 21.595731735229492, 26.23738670349121, 43.75649642944336, 73.28146362304688, 19.525665283203125, 100.52306365966797, 40.32997131347656, 29.6964111328125, 75.3953857421875, 93.181884765625, 22.507272720336914, 59.74761962890625, 21.04595947265625, 30.5830078125, 118.5794677734375, 48.582088470458984, 125.3700180053711, 65.9073257446289, 150.08973693847656, 103.46758270263672, 17.02717399597168, 35.91211700439453, 82.61681365966797, 118.71440887451172, 45.54209899902344, 59.20803451538086, 94.67938232421875, 106.31056213378906, 170.58914184570312, 40.90693664550781, 138.04324340820312, 108.37625885009766, 47.49951171875, 52.84089660644531, 44.46120071411133, 156.4938201904297, 17.328304290771484, 70.6837158203125, 100.99484252929688, 24.12629508972168, 63.74178695678711, 52.989837646484375, 16.041479110717773, 41.76425552368164, 179.85476684570312, 28.7943115234375, 32.40625, 37.30921936035156, 87.05245971679688, 71.52022552490234, 98.5990982055664, 18.521148681640625, 28.223480224609375, 110.70401763916016, 56.804500579833984, 66.78618621826172, 29.0609130859375, 262.3729248046875, 3.713312864303589, 2.663360595703125, 3.10079288482666, 1.781764030456543, 2.612321138381958, 2.346552610397339, 2.065199851989746, 2.020602226257324, 3.1882622241973877, 2.4263041019439697, 2.308506965637207, 1.6691694259643555, 3.1404716968536377, 2.226806640625, 3.21415638923645, 2.978093147277832, 3.3156614303588867, 2.673389196395874, 1.9646307229995728, 3.2510876655578613, 2.144442558288574, 2.075080156326294, 1.4399709701538086, 2.078129529953003, 2.0253348350524902, 1.6807126998901367, 1.6620397567749023, 1.824023723602295, 1.7876747846603394, 2.493411064147949, 2.597200870513916, 2.406804084777832, 1.5970619916915894, 2.7307891845703125, 2.6791787147521973, 1.721205711364746, 2.367314338684082, 2.4176137447357178, 1.5364489555358887, 1.2575421333312988, 3.1470460891723633, 1.4175764322280884, 2.0435094833374023, 2.5381999015808105, 2.1924962997436523, 1.3915642499923706, 2.686993360519409, 2.2938270568847656, 2.7063324451446533, 2.0656957626342773, 1.4926825761795044, 2.122349739074707, 2.692166328430176, 0.9704694747924805, 1.419747233390808, 3.049957752227783, 2.374345064163208, 2.498835563659668, 1.3467262983322144, 3.0517866611480713, 2.3664581775665283, 1.7521390914916992, 3.0576770305633545, 2.6537725925445557, 1.835906982421875, 2.240821599960327, 2.988280773162842, 1.5459624528884888, 2.1725075244903564, 1.0512704849243164, 2.5408735275268555, 1.4917229413986206, 1.786995768547058, 2.254394292831421, 1.4790416955947876, 1.8080507516860962, 1.744002342224121, 3.1235382556915283, 2.222916603088379, 2.374814748764038, 1.506895661354065, 2.7730541229248047, 1.4506869316101074, 3.0431816577911377, 1.610512375831604, 2.607250928878784, 2.182898998260498, 1.3781945705413818, 1.1851414442062378, 3.503028154373169, 1.919424057006836, 2.4009971618652344, 1.6558942794799805, 1.291223406791687, 2.1081042289733887, 2.2747018337249756, 1.7249619960784912, 2.4975388050079346, 1.6985044479370117, 2.908978223800659, 1.7839630842208862, 2.3985748291015625, 2.8463337421417236, 1.8739805221557617, 2.497823476791382, 2.38883113861084, 3.1285183429718018, 1.9417834281921387, 2.2823259830474854, 3.18729305267334, 3.163918972015381, 2.6631267070770264, 1.8893308639526367, 3.032465696334839, 1.4144850969314575, 1.990198016166687, 1.2497185468673706, 3.0775060653686523, 1.7874398231506348, 1.74355149269104, 1.138795256614685, 2.3320376873016357, 0.9996976852416992, 3.1733200550079346, 2.063114643096924, 2.0358457565307617, 2.106320858001709, 1.6733503341674805, 2.3376636505126953, 1.9679802656173706, 1.1380585432052612, 1.5437661409378052, 1.6307817697525024, 1.9028939008712769, 2.874840021133423, 2.1674444675445557, 1.8087362051010132, 3.77978253364563, 1.5355881452560425, 3.0351648330688477, 2.3482789993286133, 1.574681043624878, 2.0921812057495117, 2.5792880058288574, 2.1575560569763184, 2.9892895221710205, 2.1389153003692627, 3.053806781768799, 2.59238600730896, 2.2934865951538086, 2.5580334663391113, 2.0276801586151123, 2.1091699600219727, 1.4676254987716675, 1.9928878545761108, 2.2888729572296143, 1.4937925338745117, 2.3106584548950195, 2.3691015243530273, 2.160529375076294, 2.3654088973999023, 2.2846877574920654, 1.3744438886642456, 2.9049878120422363, 2.2571358680725098, 1.8637162446975708, 2.97416353225708, 1.7570542097091675, 2.426081418991089, 2.010369300842285, 1.7986139059066772, 1.323159098625183, 1.5143821239471436, 2.3558952808380127, 2.3707995414733887, 0.9898750185966492, 1.2878202199935913, 1.924230933189392, 1.6855382919311523, 2.8332855701446533, 3.301525831222534, 1.3746436834335327, 2.1849701404571533, 1.3054434061050415, 1.925063133239746, 2.1175050735473633, 1.9567224979400635, 2.086425542831421, 1.2205123901367188, 2.3970770835876465, 1.67008638381958, 2.242649555206299, 2.0702013969421387, 2.883876085281372, 3.388007164001465, 2.7218291759490967, 2.0626769065856934, 2.619717597961426, 2.4450197219848633, 2.2080202102661133, 2.131162166595459, 1.960026502609253, 2.7182531356811523, 2.6915717124938965, 2.3354926109313965, 2.3272948265075684, 2.9590518474578857, 1.9881467819213867, 3.299494504928589, 2.2188217639923096, 2.0638608932495117, 2.8513176441192627, 3.0059726238250732, 2.3672935962677, 2.161515712738037, 1.935907244682312, 2.725644111633301, 1.9824250936508179, 1.2697135210037231, 1.7020351886749268, 2.909377336502075, 2.6225082874298096, 2.2450966835021973, 3.2419707775115967, 2.688014268875122, 3.29435658454895, 2.400222063064575, 2.302180051803589, 2.2272703647613525, 3.5539989471435547, 1.8007726669311523, 3.26839542388916, 3.937250852584839, 3.381814479827881, 2.083287239074707, 1.4348249435424805, 2.997596025466919, 2.926219940185547, 1.8782039880752563, 2.899876594543457, 2.1080026626586914, 1.8030037879943848, 3.2800238132476807, 3.342658042907715, 3.467217445373535, 1.3450841903686523, 1.695473551750183, 2.108799934387207, 1.9863711595535278, 3.39587140083313, 1.9979978799819946, 1.9871948957443237, 3.1164658069610596, 1.6568344831466675, 1.676674723625183, 2.8481738567352295, 2.9916157722473145, 3.095507860183716, 1.511544108390808, 2.069436550140381, 1.660273551940918, 1.780192494392395, 3.0606157779693604, 3.378077268600464, 1.3445358276367188, 2.2344491481781006, 2.4272091388702393, 1.7652355432510376, 2.44977068901062, 2.0434350967407227, 1.0127513408660889, 3.535061836242676, 1.983569860458374, 1.680777668952942, 2.5591461658477783, 1.462706208229065, 2.077357292175293, 2.3304152488708496, 3.2123336791992188, 2.0601062774658203, 2.7443981170654297, 3.6012144088745117, 3.300614595413208, 2.518354654312134, 2.7580833435058594, 2.583892822265625, 2.6750872135162354, 2.372443437576294, 1.7868033647537231, 3.073406934738159, 1.7453231811523438, 1.7166345119476318, 3.313551664352417, 1.9569671154022217, 1.7873455286026, 3.1891021728515625, 3.5468242168426514, 2.4688022136688232, 1.9704786539077759, 1.0631237030029297, 0.14333106577396393, 0.10060811042785645, 0.13675105571746826, 0.0902269035577774, 0.1683286428451538, 0.21356135606765747, 0.14164474606513977, 0.12812887132167816, 0.1236155703663826, 0.19077910482883453, 0.11978673934936523, 0.16488660871982574, 0.15287621319293976, 0.15896044671535492, 0.12964904308319092, 0.10791461914777756, 0.15028363466262817, 0.15442311763763428, 0.15486657619476318, 0.25018757581710815, 0.1520981341600418, 0.12017357349395752, 0.140907421708107, 0.1287844032049179, 0.15984784066677094, 0.19606761634349823, 0.10007644444704056, 0.1947384625673294, 0.1165873184800148, 0.1256774663925171, 0.10684831440448761, 0.10768812149763107, 0.12569133937358856, 0.10027637332677841, 0.1630217581987381, 0.10167092829942703, 0.14161747694015503, 0.08312489092350006, 0.08448515087366104, 0.12847991287708282, 0.129830464720726, 0.13637611269950867, 0.04235747084021568, 0.15937140583992004, 0.15934838354587555, 0.05959494411945343, 0.13493750989437103, 0.1857553869485855, 0.18125887215137482, 0.11532764881849289, 0.12292692810297012, 0.12934279441833496, 0.1039653867483139, 0.0990775004029274, 0.11947246640920639, 0.11391987651586533, 0.15937690436840057, 0.16617250442504883, 0.08928096294403076, 0.11570533365011215, 0.15902221202850342, 0.13561517000198364, 0.12990736961364746, 0.13892166316509247, 0.10103733092546463, 0.1552836149930954, 0.11440740525722504, 0.06286507844924927, 0.15663716197013855, 0.18989889323711395, 0.1380854696035385, 0.1464725136756897, 0.16215603053569794, 0.07679904997348785, 0.18417520821094513, 0.14974747598171234, 0.08967693150043488, 0.07589209079742432, 0.16952045261859894, 0.12676052749156952, 0.12856458127498627, 0.16952407360076904, 0.16174907982349396, 0.13327360153198242, 0.15287242829799652, 0.17004217207431793, 0.12854260206222534, 0.1645471155643463, 0.15934500098228455, 0.14109133183956146, 0.13926993310451508, 0.10665126889944077, 0.1368565708398819, 0.09794208407402039, 0.20901606976985931, 0.1514144241809845, 0.15333342552185059, 0.1256263256072998, 0.10920194536447525, 0.13712234795093536, 0.08793041110038757, 0.13016343116760254, 0.08400426059961319, 0.20235851407051086, 0.14818736910820007, 0.16058480739593506, 0.04505852609872818, 0.20550143718719482, 0.0867147222161293, 0.14593052864074707, 0.1485845446586609, 0.08980721235275269, 0.1612134575843811, 0.15957996249198914, 0.13804033398628235, 0.16370627284049988, 0.16212144494056702, 0.10980702191591263, 0.07290090620517731, 0.17223019897937775, 0.14144116640090942, 0.10059960931539536, 0.14865979552268982, 0.15646883845329285, 0.0823020190000534, 0.12308170646429062, 0.13513648509979248, 0.17230738699436188, 0.1634604036808014, 0.13097035884857178, 0.1268850415945053, 0.12569159269332886, 0.13298097252845764, 0.15203222632408142, 0.10083997249603271, 0.11686377972364426, 0.1873094141483307, 0.10236280411481857, 0.15549540519714355, 0.06092298775911331, 0.16600355505943298, 0.14684399962425232, 0.1510588675737381, 0.13087615370750427, 0.13227438926696777, 0.06976401805877686, 0.16181965172290802, 0.10666745901107788, 0.10664750635623932, 0.1720731258392334, 0.13233113288879395, 0.2086038589477539, 0.11204404383897781, 0.09495208412408829, 0.10425858944654465, 0.12446778267621994, 0.13078300654888153, 0.09625988453626633, 0.17997661232948303, 0.15986795723438263, 0.09606420248746872, 0.14508529007434845, 0.1696336269378662, 0.1691758632659912, 0.12468097358942032, 0.11905261129140854, 0.1464901864528656, 0.1755661517381668, 0.13701510429382324, 0.12562298774719238, 0.1654166728258133, 0.1571049690246582, 0.0990808978676796, 0.11121080070734024, 0.1792391538619995, 0.09137191623449326, 0.11770228296518326, 0.10334121435880661, 0.13062012195587158, 0.16971786320209503, 0.18358905613422394, 0.07147020846605301, 0.14479582011699677, 0.15244780480861664, 0.06944411993026733, 0.13752511143684387, 0.13726794719696045, 0.1425367295742035, 0.08790687471628189, 0.13277560472488403, 0.17315906286239624, 0.14983950555324554, 0.1285707652568817, 0.12280948460102081, 0.10450618714094162, 0.1637132167816162, 0.12943321466445923, 0.13023926317691803, 0.15081489086151123, 0.13665840029716492, 0.1467643678188324, 0.1428208351135254, 0.19277912378311157, 0.09269361943006516, 0.063605897128582, 0.14347712695598602, 0.12698307633399963, 0.16291995346546173, 0.13184498250484467, 0.09957003593444824, 0.10022193938493729, 0.08332685381174088, 0.11177098751068115, 0.07272535562515259, 0.05956602469086647, 0.11469485610723495, 0.1386890411376953, 0.1275954246520996, 0.08125823736190796, 0.09741376340389252, 0.15885531902313232, 0.1593271642923355, 0.10540282726287842, 0.1807813048362732, 0.21436449885368347, 0.1424400359392166, 0.04670671373605728, 0.1807154417037964, 0.2020421177148819, 0.15036731958389282, 0.05926854535937309, 0.05677156150341034, 0.12007438391447067, 0.1232442632317543, 0.06920742988586426, 0.2655382752418518, 0.0937507152557373, 0.07804057747125626, 0.14262336492538452, 0.1784231960773468, 0.2041059285402298, 0.16795678436756134, 0.15126889944076538, 0.09017843008041382, 0.10773637890815735, 0.16079211235046387, 0.1147271916270256, 0.1429576277732849, 0.17534099519252777, 0.1513652354478836, 0.13780838251113892, 0.1299009919166565, 0.08974940329790115, 0.08110164105892181, 0.11628367751836777, 0.10432840138673782, 0.19436830282211304, 0.049587201327085495, 0.10834479331970215, 0.16197097301483154, 0.08021831512451172, 0.14402839541435242, 0.16529223322868347, 0.15289399027824402, 0.15852488577365875, 0.21752965450286865, 0.13123583793640137, 0.19560851156711578, 0.14174360036849976, 0.1706968992948532, 0.11840282380580902, 0.12698999047279358, 0.13823091983795166, 0.14913307130336761, 0.05479228496551514, 0.0896744355559349, 0.07696989923715591, 0.10166894644498825, 0.13689592480659485, 0.09212760627269745, 0.08234405517578125, 0.16192050278186798, 0.05504247546195984, 0.20070555806159973, 0.1701786071062088, 0.12002677470445633, 0.06758751720190048, 0.08860786259174347, 0.11649951338768005, 0.09559884667396545, 0.09847478568553925, 0.1634048968553543, 0.1162332147359848, 0.11652667820453644, 0.18585944175720215, 0.11029919981956482, 0.12314701080322266, 0.13952258229255676, 0.10324668884277344, 0.07585206627845764, 0.5634620785713196, 1.0065150260925293, 1.137538194656372, 1.2150216102600098, 0.7198254466056824, 0.6940445303916931, 1.0126832723617554, 0.8249545097351074, 1.2570955753326416, 1.4143825769424438, 1.7306313514709473, 0.9640893340110779, 1.088950514793396, 0.7313653230667114, 0.6538699269294739, 0.9664369225502014, 0.6599859595298767, 0.5915766954421997, 1.0121580362319946, 0.9975548982620239, 0.8418615460395813, 1.3771320581436157, 0.6848823428153992, 0.9180882573127747, 0.5341572165489197, 0.6256580948829651, 0.7796908617019653, 1.3865108489990234, 1.0473792552947998, 0.8191621899604797, 0.7019006013870239, 0.7526111602783203, 1.3260809183120728, 0.7968158721923828, 0.7056320309638977, 0.7510462999343872, 0.8786115646362305, 1.2284785509109497, 1.2807940244674683, 1.9664291143417358, 1.1198550462722778, 0.9104596376419067, 1.108620524406433, 0.9152036905288696, 0.5872928500175476, 1.094926118850708, 1.1226369142532349, 0.6517364382743835, 1.948607087135315, 0.7468090057373047, 0.7712512016296387, 1.4480149745941162, 0.9887393116950989, 0.9313170909881592, 1.2197692394256592, 0.8395918011665344, 0.32765278220176697, 0.792491614818573, 0.5977543592453003, 1.2369122505187988, 0.9926368594169617, 0.7052157521247864, 0.8929798603057861, 0.5791693925857544, 0.5357289910316467, 0.7252880930900574, 0.694341778755188, 0.8078015446662903, 0.4571123719215393, 1.133941650390625, 0.8251412510871887, 1.0813959836959839, 1.0390962362289429, 1.0159571170806885, 1.2084450721740723, 0.6390573978424072, 1.0477404594421387, 1.1334203481674194, 1.1426615715026855, 0.9284073710441589, 0.7241706848144531, 1.0968900918960571, 1.019333004951477, 1.0388474464416504, 0.8101317882537842, 1.8732458353042603, 0.9333834648132324, 0.9097071886062622, 0.5327838063240051, 1.1500747203826904, 1.2945550680160522, 0.776189386844635, 0.8268894553184509, 0.5602990388870239, 0.5573826432228088, 1.0363218784332275, 0.9401333332061768, 0.8435677886009216, 0.8553276062011719, 1.2203118801116943, 1.0825309753417969, 0.6785395741462708, 0.8989995121955872, 1.0462536811828613, 0.9200164675712585, 0.741737961769104, 1.2786774635314941, 0.6373432874679565, 1.5091179609298706, 0.8028144836425781, 0.8250177502632141, 0.4911743700504303, 1.3500540256500244, 0.8097226023674011, 1.4109047651290894, 1.0919649600982666, 1.0682119131088257, 0.7798808217048645, 1.0532280206680298, 1.116458535194397, 0.649526834487915, 1.4452546834945679, 1.0607728958129883, 1.113282322883606, 0.579315721988678, 0.6326417326927185, 0.7301895022392273, 0.8157812356948853, 1.4019020795822144, 1.1761733293533325, 0.7731066942214966, 1.0258588790893555, 0.9430676698684692, 0.7602341771125793, 0.622803270816803, 0.7790858149528503, 0.7520319223403931, 0.33823996782302856, 0.5038024187088013, 0.5998319387435913, 1.4975931644439697, 0.9219347834587097, 0.6033830642700195, 0.637662410736084, 0.5860024690628052, 1.3938522338867188, 0.8440481424331665, 1.0794521570205688, 0.679627537727356, 0.9184455871582031, 0.7120466232299805, 1.0223355293273926, 0.8119001388549805, 1.458593726158142, 1.1227258443832397, 1.1013340950012207, 1.2608661651611328, 1.2304139137268066, 0.7442043423652649, 1.3048479557037354, 0.9368546605110168, 1.9576084613800049, 0.892512321472168, 0.844897449016571, 1.0191328525543213, 0.7499886751174927, 0.7319919466972351, 0.4943055510520935, 0.6868214011192322, 0.8401509523391724, 0.6980447173118591, 1.3860251903533936, 0.5799697637557983, 0.6274921894073486, 0.4703229069709778, 0.7424067258834839, 1.2874202728271484, 0.5262534618377686, 0.8778471946716309, 1.4321459531784058, 0.6892999410629272, 0.8174087405204773, 1.1217870712280273, 1.2344790697097778, 1.2563930749893188, 1.3910534381866455, 0.9698209762573242, 0.6939318776130676, 0.8951138257980347, 0.6356961131095886, 0.7749508619308472, 1.0974253416061401, 0.8287348747253418, 1.0595755577087402, 1.5144424438476562, 0.23412279784679413, 0.9610511660575867, 0.9501972198486328, 0.7287160158157349, 0.7851772308349609, 0.9688981175422668, 1.6196717023849487, 0.5387884378433228, 0.7309718132019043, 0.9305920004844666, 0.8425061106681824, 0.5178532004356384, 0.6993435621261597, 0.9605792164802551, 0.9037135243415833, 0.9245150685310364, 1.1360077857971191, 0.9667991995811462, 0.9231126308441162, 1.1793465614318848, 0.900593101978302, 0.6022239327430725, 0.7879315614700317, 0.9576574563980103, 0.9253698587417603, 1.1141884326934814, 1.1288485527038574, 1.1820547580718994, 1.4502220153808594, 1.1870441436767578, 1.5175437927246094, 0.612407922744751, 0.8995362520217896, 1.3054500818252563, 1.0510730743408203, 0.45965275168418884, 0.9998682141304016, 1.7057125568389893, 1.0684685707092285, 0.6344353556632996, 1.430875539779663, 1.06312894821167, 1.2409354448318481, 0.8684418797492981, 1.3912203311920166, 1.0194954872131348, 1.0319156646728516, 0.9032872319221497, 0.741768479347229, 0.9811055064201355, 0.990472674369812, 0.608257532119751, 0.4986203908920288, 0.9717034697532654, 1.0872516632080078, 0.5196971297264099, 0.8547055125236511, 0.8952770233154297, 1.0994930267333984, 0.731812596321106, 1.1774674654006958, 1.3836642503738403, 0.8002685904502869, 0.6586030721664429, 0.42005816102027893, 0.9723580479621887, 0.9641940593719482, 1.1308830976486206, 1.1082438230514526, 1.4363508224487305, 0.9394381642341614, 0.8447033762931824, 1.0630669593811035, 0.714788556098938, 0.7182862162590027, 0.6883054971694946, 0.664376974105835, 0.611410915851593, 0.8595224022865295, 0.8146880269050598, 0.801936149597168, 1.2427904605865479, 1.2366905212402344, 1.4029041528701782, 1.0866502523422241, 0.7651435732841492, 0.6724507212638855, 0.7920900583267212, 1.0516334772109985, 0.7619174122810364, 1.1313624382019043, 0.6213782429695129, 0.6685410737991333, 1.2994390726089478, 1.0239815711975098, 0.8860076069831848, 1.9256044626235962, 0.6723238229751587, 0.9156408309936523, 0.7792940139770508, 0.688568115234375, 0.8918048143386841, 1.1565529108047485, 0.8232400417327881, 0.7148568034172058, 42.29539108276367, 27.28363800048828, 106.70616912841797, 103.68472290039062, 46.61147689819336, 138.73533630371094, 20.452402114868164, 53.55646514892578, 11.52484130859375, 118.4622802734375, 23.705322265625, 63.59637451171875, 52.39004135131836, 70.29373168945312, 94.9369125366211, 67.42239379882812, 49.770263671875, 47.52334213256836, 68.48143768310547, 40.26736068725586, 27.078704833984375, 104.23038482666016, 53.176361083984375, 55.422332763671875, 105.10726928710938, 35.21284484863281, 98.37699127197266, 18.196136474609375, 21.92559814453125, 126.07012176513672, 126.74534606933594, 59.970272064208984, 22.431884765625, 56.2828369140625, 45.36932373046875, 139.48944091796875, 21.404603958129883, 121.37090301513672, 30.69915771484375, 37.08024215698242, 37.394447326660156, 72.09258270263672, 73.0645751953125, 28.195585250854492, 158.30091857910156, 85.95623779296875, 93.50311279296875, 25.08850860595703, 106.5941390991211, 50.31098556518555, 98.09893035888672, 23.8485107421875, 77.85549926757812, 21.87456512451172, 275.7636413574219, 54.5942268371582, 24.54732894897461, 18.234710693359375, 30.89691162109375, 130.46934509277344, 74.44549560546875, 79.805419921875, 134.331298828125, 73.81522369384766, 72.13766479492188, 20.501649856567383, 28.1636962890625, 96.9177017211914, 91.36677551269531, 41.091609954833984, 164.2664031982422, 150.512451171875, 27.015775680541992, 37.00494384765625, 18.211347579956055, 143.53009033203125, 28.698881149291992, 40.27067947387695, 84.11404418945312, 89.76583099365234, 87.50090026855469, 48.79246139526367, 20.860076904296875, 57.703826904296875, 33.513370513916016, 29.585100173950195, 75.7950439453125, 91.87993621826172, 20.995849609375, 48.9093017578125, 115.21372985839844, 39.75909423828125, 45.215145111083984, 15.354400634765625, 38.17275619506836, 165.42092895507812, 66.72379302978516, 132.75634765625, 38.56217956542969, 87.31302642822266, 89.96593475341797, 71.61945343017578, 57.165740966796875, 144.11260986328125, 119.03662109375, 106.13201904296875, 63.7371826171875, 96.30571746826172, 81.7333984375, 76.81275939941406, 67.65597534179688, 74.01106262207031, 108.78423309326172, 78.70858001708984, 36.11738967895508, 43.877742767333984, 177.5882568359375, 32.4034423828125, 51.60994338989258, 79.39287567138672, 82.20387268066406, 84.57939910888672, 28.267038345336914, 68.05126953125, 110.97097778320312, 60.54323959350586, 69.99481964111328, 48.048622131347656, 91.52042388916016, 35.312255859375, 47.13971710205078, 125.05746459960938, 30.768768310546875, 64.81107330322266, 33.9464111328125, 27.69908905029297, 30.261276245117188, 16.047882080078125, 27.479740142822266, 60.53432846069336, 37.85759735107422, 73.91460418701172, 134.04885864257812, 21.716554641723633, 73.18629455566406, 57.0443115234375, 20.742340087890625, 17.227863311767578, 73.73809051513672, 38.200439453125, 41.30986404418945, 141.6669464111328, 111.97140502929688, 95.37925720214844, 41.539520263671875, 90.73125457763672, 63.12333679199219, 36.97853469848633, 42.98577117919922, 103.263427734375, 26.61795997619629, 213.71250915527344, 136.5804443359375, 141.49209594726562, 22.6739501953125, 60.064788818359375, 57.36586380004883, 37.995086669921875, 140.4329833984375, 91.5228271484375, 75.67586517333984, 29.46489906311035, 62.4189453125, 70.90532684326172, 59.576297760009766, 96.68722534179688, 100.66646575927734, 37.9666748046875, 15.996003150939941, 152.56930541992188, 19.31170654296875, 35.08958435058594, 23.62422752380371, 77.36866760253906, 83.12714385986328, 15.376617431640625, 58.928802490234375, 108.9994888305664, 81.06625366210938, 12.251983642578125, 147.63436889648438, 19.56951904296875, 77.51593780517578, 83.6116943359375, 57.8702392578125, 22.887451171875, 82.6576156616211, 19.64447784423828, 125.56561279296875, 62.533660888671875, 68.88166809082031, 57.6302490234375, 80.012939453125, 66.80795288085938, 58.31187438964844, 20.233924865722656, 59.06059265136719, 81.35028076171875, 30.61370849609375, 100.53515625, 124.85951232910156, 40.111576080322266, 58.932098388671875, 63.87417221069336, 15.451019287109375, 26.565399169921875, 40.948577880859375, 72.37281799316406, 101.68315887451172, 93.9090576171875, 78.75078582763672, 97.63601684570312, 102.2108154296875, 56.1466064453125, 64.4676513671875, 106.30581665039062, 41.90867233276367, 73.10752868652344, 80.10189819335938, 58.71744918823242, 102.6175537109375, 31.671415328979492, 37.52553939819336, 65.65536499023438, 115.11062622070312, 60.46768569946289, 143.6976776123047, 71.72430419921875, 79.71510314941406, 69.32284545898438, 28.80756950378418, 115.97039794921875, 34.768280029296875, 54.99184799194336, 52.24100112915039, 63.261512756347656, 53.11398696899414, 27.758817672729492, 25.412294387817383, 58.24090576171875, 65.955810546875, 52.70130920410156, 112.58259582519531, 24.797367095947266, 62.62196731567383, 52.08901596069336, 98.98745727539062, 84.56802368164062, 72.01907348632812, 82.38787841796875, 36.71368408203125, 139.87527465820312, 26.988798141479492, 147.27938842773438, 50.10036849975586, 54.85256576538086, 53.322479248046875, 53.70547103881836, 84.54866790771484, 20.21795654296875, 16.563705444335938, 73.71139526367188, 157.18988037109375, 20.559982299804688, 19.6978759765625, 31.56180763244629, 31.276702880859375, 91.10833740234375, 66.63249206542969, 26.337257385253906, 47.76982498168945, 60.90859603881836, 125.12763214111328, 36.5185546875, 106.69095611572266, 33.41738510131836, 66.87417602539062, 36.55450439453125, 68.39849090576172, 93.61354064941406, 66.72918701171875, 18.973026275634766, 90.10607147216797, 135.33668518066406, 29.33660888671875, 68.28748321533203, 18.387176513671875, 70.077392578125, 20.680213928222656, 100.9435043334961, 2.6381425857543945, 2.7111568450927734, 2.751216173171997, 2.2210681438446045, 2.196661949157715, 1.7936196327209473, 2.8069372177124023, 2.2106847763061523, 2.83351993560791, 1.890702486038208, 2.165860176086426, 1.7837481498718262, 1.6475571393966675, 2.5365936756134033, 2.1909232139587402, 1.969645619392395, 1.763270378112793, 2.117569923400879, 2.426666736602783, 2.13918399810791, 1.7602479457855225, 3.431035041809082, 2.773007869720459, 2.621781826019287, 1.9442319869995117, 2.121342420578003, 3.002344846725464, 1.970872163772583, 2.306809425354004, 2.2480480670928955, 2.120954751968384, 1.8504095077514648, 2.112712860107422, 2.1151158809661865, 1.5615415573120117, 1.434679388999939, 1.50493323802948, 1.7915769815444946, 2.6721181869506836, 1.5315093994140625, 3.021618604660034, 2.334867238998413, 1.8542486429214478, 3.575573682785034, 2.0968053340911865, 2.533430814743042, 2.704584836959839, 2.2343127727508545, 2.670414924621582, 2.7232162952423096, 2.2083613872528076, 2.956691265106201, 2.1863813400268555, 1.1731406450271606, 2.8165347576141357, 1.2221022844314575, 2.764312744140625, 1.4387176036834717, 1.24339759349823, 3.4705333709716797, 2.76370906829834, 1.5886276960372925, 1.8939924240112305, 1.6487674713134766, 1.634846568107605, 2.9407219886779785, 1.7890241146087646, 1.4224157333374023, 1.6328203678131104, 2.45809006690979, 2.1088037490844727, 1.7573097944259644, 1.449892520904541, 2.202444076538086, 1.6852315664291382, 2.1868553161621094, 3.105088472366333, 2.1089887619018555, 2.07973575592041, 3.5209221839904785, 1.7032723426818848, 2.376694917678833, 2.1462154388427734, 1.600752830505371, 3.0527966022491455, 2.0285749435424805, 2.3930959701538086, 1.9891902208328247, 3.32084584236145, 2.4856107234954834, 1.5377930402755737, 2.3948452472686768, 2.7281737327575684, 2.333209753036499, 2.752333402633667, 2.449875831604004, 2.4385082721710205, 2.148235321044922, 2.4271597862243652, 1.8277825117111206, 2.4954257011413574, 2.258206367492676, 2.3973894119262695, 3.1681108474731445, 2.05073881149292, 3.3509843349456787, 2.2373125553131104, 2.204953670501709, 2.1626696586608887, 1.598530650138855, 1.4871206283569336, 2.6113078594207764, 1.708357810974121, 1.2313554286956787, 1.6794042587280273, 1.4385671615600586, 3.0913467407226562, 3.2675983905792236, 1.0647454261779785, 1.782282829284668, 2.974292039871216, 1.156296730041504, 2.6441779136657715, 1.717569351196289, 1.185610055923462, 1.6396797895431519, 1.648444652557373, 2.1671881675720215, 1.7919892072677612, 1.5389924049377441, 1.2513703107833862, 2.605379581451416, 2.850987672805786, 1.9115726947784424, 3.1548681259155273, 3.478614091873169, 1.629825234413147, 1.6212433576583862, 2.813520669937134, 2.0651025772094727, 2.3449580669403076, 1.8830351829528809, 2.468939781188965, 2.091063976287842, 1.3186521530151367, 2.135802984237671, 3.4210293292999268, 3.338128089904785, 2.097062110900879, 1.8940763473510742, 2.0222220420837402, 3.0796642303466797, 2.8385112285614014, 2.829014539718628, 1.7249153852462769, 2.7691197395324707, 1.9955854415893555, 1.5953856706619263, 2.460139513015747, 2.160886287689209, 2.4772653579711914, 1.639891505241394, 2.2562122344970703, 1.6841312646865845, 3.023549795150757, 3.6544058322906494, 2.513636589050293, 2.12032413482666, 1.857592225074768, 2.844774007797241, 2.4178285598754883, 2.034663677215576, 3.836554527282715, 1.655421257019043, 2.368353843688965, 2.9614415168762207, 2.8287670612335205, 1.2315294742584229, 2.7322494983673096, 2.8640358448028564, 1.9391121864318848, 2.5826148986816406, 2.4151885509490967, 3.123927354812622, 1.9882491827011108, 1.433327555656433, 3.0497331619262695, 2.2496232986450195, 2.2553162574768066, 3.1535351276397705, 3.375732660293579, 2.0478758811950684, 2.802509307861328, 1.6833982467651367, 3.434054374694824, 1.95457923412323, 2.7316014766693115, 2.806678056716919, 2.092207908630371, 2.381460189819336, 2.227604866027832, 1.5020904541015625, 2.3404529094696045, 2.784308671951294, 2.720949649810791, 2.8085930347442627, 2.4631154537200928, 1.2720235586166382, 3.2263076305389404, 2.273637533187866, 1.8262336254119873, 2.575274705886841, 2.424967050552368, 3.263744354248047, 3.0178375244140625, 1.6494683027267456, 1.1170743703842163, 2.461975574493408, 2.055413246154785, 2.309497117996216, 1.990303874015808, 1.3731441497802734, 3.188755989074707, 1.759316325187683, 3.234013795852661, 2.974762439727783, 2.76444149017334, 2.4948530197143555, 2.270573616027832, 2.2725093364715576, 1.7837952375411987, 1.9745341539382935, 2.859769821166992, 1.6195042133331299, 2.3547236919403076, 1.9971320629119873, 2.9388844966888428, 2.711179256439209, 2.419186592102051, 1.3604671955108643, 2.3227548599243164, 1.9774428606033325, 1.4944884777069092, 2.435553550720215, 2.8661444187164307, 2.977748155593872, 3.035722494125366, 2.9744904041290283, 1.7578715085983276, 2.875781297683716, 2.695200204849243, 2.666386365890503, 2.569027900695801, 2.7663609981536865, 2.767899751663208, 2.6048905849456787, 1.737386703491211, 2.4278154373168945, 3.0017638206481934, 1.9213132858276367, 2.7266902923583984, 1.2304329872131348, 3.0105342864990234, 2.0644619464874268, 1.9282019138336182, 0.9397077560424805, 2.9729340076446533, 2.654510498046875, 1.717926263809204, 3.9317119121551514, 1.7939919233322144, 2.3825645446777344, 1.5623825788497925, 1.8197095394134521, 2.733020305633545, 1.7676857709884644, 2.092132329940796, 2.868548631668091, 2.3018171787261963, 1.9864662885665894, 1.8275219202041626, 1.3407601118087769, 2.215400218963623, 1.0810097455978394, 2.1800665855407715, 1.8866432905197144, 1.7517833709716797, 3.011446475982666, 2.0864012241363525, 1.761407732963562, 2.3454010486602783, 2.9737517833709717, 2.876689910888672, 2.2434115409851074, 2.6903927326202393, 2.1216042041778564, 3.8044378757476807, 2.1678013801574707, 1.832336664199829, 2.064549446105957, 0.16305772960186005, 0.11026990413665771, 0.1526617854833603, 0.12207482010126114, 0.20943880081176758, 0.16941297054290771, 0.11241590231657028, 0.1106337308883667, 0.11878112703561783, 0.15148687362670898, 0.15103314816951752, 0.23541484773159027, 0.11506398022174835, 0.15465126931667328, 0.14641328155994415, 0.13445787131786346, 0.2088901400566101, 0.12787748873233795, 0.07256775349378586, 0.2588873505592346, 0.054461363703012466, 0.09911320358514786, 0.2110239416360855, 0.23463718593120575, 0.15019996464252472, 0.10456013679504395, 0.04516836628317833, 0.1943320780992508, 0.14601154625415802, 0.09199094772338867, 0.14536339044570923, 0.17587049305438995, 0.13472968339920044, 0.1762983351945877, 0.08533141762018204, 0.1965002566576004, 0.19659845530986786, 0.07537758350372314, 0.1270749419927597, 0.1890510469675064, 0.10980510711669922, 0.1178407147526741, 0.09535329788923264, 0.0796450525522232, 0.17333856225013733, 0.1679491400718689, 0.06847882270812988, 0.1526023894548416, 0.1255020946264267, 0.18175262212753296, 0.14460641145706177, 0.1260508894920349, 0.11191903799772263, 0.10496429353952408, 0.07689787447452545, 0.1624184399843216, 0.19322049617767334, 0.14115233719348907, 0.20670770108699799, 0.12888534367084503, 0.08705110102891922, 0.1034875214099884, 0.1604543775320053, 0.1052316427230835, 0.10963630676269531, 0.12008094787597656, 0.24514763057231903, 0.2172568142414093, 0.13979022204875946, 0.06646764278411865, 0.08549413830041885, 0.17411787807941437, 0.1649889349937439, 0.11647842824459076, 0.14964859187602997, 0.17307138442993164, 0.1420898586511612, 0.19803841412067413, 0.07480873167514801, 0.12739484012126923, 0.1540198028087616, 0.21987943351268768, 0.13984277844429016, 0.11338017880916595, 0.12275959551334381, 0.08521987497806549, 0.12438137084245682, 0.06839270144701004, 0.08596783131361008, 0.2078426331281662, 0.09043765813112259, 0.15173973143100739, 0.06867028027772903, 0.06632738560438156, 0.15238305926322937, 0.13714128732681274, 0.11607895791530609, 0.07057525962591171, 0.12379908561706543, 0.16742682456970215, 0.1375666707754135, 0.09349209815263748, 0.21490085124969482, 0.1399427205324173, 0.09587100893259048, 0.1746198683977127, 0.10446695983409882, 0.15873503684997559, 0.1882760375738144, 0.1651608645915985, 0.0709737092256546, 0.09909919649362564, 0.08024382591247559, 0.09137928485870361, 0.1783289909362793, 0.1777595728635788, 0.11557593196630478, 0.14400671422481537, 0.09688764065504074, 0.14625988900661469, 0.11927196383476257, 0.2033393383026123, 0.16816726326942444, 0.15983790159225464, 0.13207364082336426, 0.13417774438858032, 0.10664619505405426, 0.14097772538661957, 0.14498001337051392, 0.09165942668914795, 0.11195746809244156, 0.07802164554595947, 0.14394713938236237, 0.1945124715566635, 0.2008102685213089, 0.09552236646413803, 0.24961405992507935, 0.19673655927181244, 0.1048797219991684, 0.14058521389961243, 0.1992233246564865, 0.06899090856313705, 0.1268271803855896, 0.10613417625427246, 0.10004426538944244, 0.12908923625946045, 0.13951458036899567, 0.11853614449501038, 0.07462996989488602, 0.11970388144254684, 0.13027478754520416, 0.0786944106221199, 0.11519435793161392, 0.11476480960845947, 0.13955429196357727, 0.1386425644159317, 0.073483906686306, 0.21081501245498657, 0.12891696393489838, 0.1365196257829666, 0.10460448265075684, 0.11055818200111389, 0.15840934216976166, 0.17409734427928925, 0.11165773123502731, 0.13607501983642578, 0.09399683028459549, 0.08604796230792999, 0.22494345903396606, 0.1293793022632599, 0.22528983652591705, 0.13961654901504517, 0.16536925733089447, 0.11067815870046616, 0.1959875375032425, 0.148823544383049, 0.11109283566474915, 0.1063324511051178, 0.10503888130187988, 0.08460614830255508, 0.16858027875423431, 0.16863401234149933, 0.1088467389345169, 0.21562686562538147, 0.1302156001329422, 0.09390678256750107, 0.09555622935295105, 0.17590735852718353, 0.141387939453125, 0.13876259326934814, 0.10822860151529312, 0.12215924263000488, 0.13866758346557617, 0.15215596556663513, 0.15194645524024963, 0.17171965539455414, 0.1570959836244583, 0.17596645653247833, 0.099835604429245, 0.2099170684814453, 0.1014721542596817, 0.11171593517065048, 0.07233835756778717, 0.11352434754371643, 0.20212459564208984, 0.11577145010232925, 0.10365500301122665, 0.15759579837322235, 0.12400674819946289, 0.0829492136836052, 0.17258915305137634, 0.1513427346944809, 0.17655767500400543, 0.12391790002584457, 0.13913273811340332, 0.10413788259029388, 0.13478673994541168, 0.13882236182689667, 0.13098645210266113, 0.1459859311580658, 0.08851239085197449, 0.1459311693906784, 0.1297508329153061, 0.1854812651872635, 0.08000506460666656, 0.1433502584695816, 0.21651431918144226, 0.16180507838726044, 0.06100137531757355, 0.13344262540340424, 0.18424129486083984, 0.056551653891801834, 0.14930298924446106, 0.06729287654161453, 0.16155913472175598, 0.17409789562225342, 0.14368851482868195, 0.19757519662380219, 0.1259482353925705, 0.10002882033586502, 0.13155497610569, 0.12987391650676727, 0.20291893184185028, 0.156632199883461, 0.16241440176963806, 0.1285681277513504, 0.18783684074878693, 0.14471864700317383, 0.05939320847392082, 0.11780957132577896, 0.11848625540733337, 0.1297793686389923, 0.17860400676727295, 0.15636515617370605, 0.1363372802734375, 0.14801782369613647, 0.2190193384885788, 0.21346671879291534, 0.11689352989196777, 0.1467975378036499, 0.14552609622478485, 0.12174954265356064, 0.09724151343107224, 0.08807764202356339, 0.11192186921834946, 0.12686914205551147, 0.13393671810626984, 0.09623957425355911, 0.14259187877178192, 0.0978800356388092, 0.13735660910606384, 0.1529363989830017, 0.17025206983089447, 0.18771854043006897, 0.1873919665813446, 0.09252800047397614, 0.05516668036580086, 0.08248121291399002, 0.16182872653007507, 0.08643589913845062, 0.0823407918214798, 0.15262028574943542, 0.12532983720302582, 0.19213147461414337, 0.1175042986869812, 0.04266125708818436, 0.09832506626844406, 0.13531199097633362, 0.2209286391735077, 0.1910434067249298, 0.1931867152452469, 0.13837336003780365, 0.1741853654384613, 0.13558737933635712, 0.20612983405590057, 0.18415336310863495, 0.13161516189575195, 0.2074938863515854, 0.10203295201063156, 0.09419874101877213, 1.0321218967437744, 1.0013511180877686, 1.1248197555541992, 1.173341989517212, 0.9068167805671692, 1.987973928451538, 1.0356078147888184, 1.0879110097885132, 1.205576777458191, 1.265796422958374, 0.7833326458930969, 1.303733468055725, 0.7469445466995239, 0.5679696798324585, 0.5314416885375977, 1.672271728515625, 0.703163743019104, 0.7415292859077454, 1.352095603942871, 1.1075493097305298, 1.4285677671432495, 0.9219753742218018, 1.1212007999420166, 0.9686579704284668, 0.7722517251968384, 0.984337568283081, 0.8303095102310181, 1.104958176612854, 1.085477352142334, 1.450714111328125, 0.8908656239509583, 1.2893857955932617, 1.0597589015960693, 1.0170682668685913, 0.9676203727722168, 0.7629455924034119, 1.1204655170440674, 1.2275501489639282, 0.872982919216156, 0.7275285124778748, 0.7139310836791992, 0.7130324244499207, 0.6856167316436768, 0.8331117033958435, 0.7755911946296692, 0.695107102394104, 0.5262132883071899, 1.2540295124053955, 1.0412771701812744, 1.0560755729675293, 0.716255784034729, 1.5160257816314697, 0.7089391946792603, 1.2719483375549316, 0.6610920429229736, 1.2326961755752563, 0.6230188608169556, 0.8366166353225708, 0.7632682919502258, 1.052384614944458, 1.1834354400634766, 0.9460404515266418, 1.2454274892807007, 0.8896563649177551, 0.609934389591217, 1.463533639907837, 0.9043931365013123, 1.2290103435516357, 1.1252052783966064, 0.9811114072799683, 1.2050471305847168, 1.1592763662338257, 0.539111852645874, 1.012513279914856, 0.7283079624176025, 0.8115022778511047, 1.1670191287994385, 0.7231235504150391, 1.2091076374053955, 0.7714329957962036, 1.211801528930664, 1.5725513696670532, 2.1249327659606934, 0.7891821265220642, 1.0843873023986816, 0.5205889344215393, 0.6939154863357544, 1.2089413404464722, 0.8746456503868103, 0.906735897064209, 0.6988309025764465, 0.662261962890625, 0.7002137303352356, 0.9775145649909973, 0.974787712097168, 0.8049584627151489, 1.190342664718628, 1.460253357887268, 1.0418572425842285, 0.8593708872795105, 0.5841337442398071, 1.1386823654174805, 0.6839439272880554, 1.228957176208496, 1.1013401746749878, 1.1502197980880737, 1.3696200847625732, 1.2906103134155273, 1.5143241882324219, 0.833746075630188, 1.4312629699707031, 0.6128740310668945, 0.8623369336128235, 1.106180191040039, 1.04715096950531, 1.373713493347168, 0.9284892082214355, 1.438002586364746, 0.929752767086029, 1.0205153226852417, 0.8459441661834717, 1.4254387617111206, 1.1753934621810913, 1.1635795831680298, 1.657356858253479, 1.2044508457183838, 0.7427005767822266, 1.2482235431671143, 0.5624561309814453, 0.8055381774902344, 0.7883432507514954, 0.9118884205818176, 1.107409954071045, 1.0665698051452637, 1.704671859741211, 1.1109575033187866, 0.8899133801460266, 1.4119749069213867, 1.158711314201355, 1.1724931001663208, 0.5573806166648865, 0.7376161813735962, 1.8624813556671143, 0.38957479596138, 0.7914892435073853, 0.6500378847122192, 0.5971950888633728, 1.5404311418533325, 1.1444202661514282, 1.8552049398422241, 1.4515647888183594, 0.5918532609939575, 1.094970703125, 0.8226902484893799, 0.6365868449211121, 0.6927230954170227, 0.7766696214675903, 0.7447399497032166, 0.8046886324882507, 0.5460491180419922, 0.9128193259239197, 1.1968717575073242, 0.7577728629112244, 1.4682106971740723, 0.6362570524215698, 1.1639896631240845, 0.970280110836029, 0.6957635879516602, 0.5348361730575562, 1.2808655500411987, 1.9194988012313843, 1.1212655305862427, 1.2764859199523926, 1.414727807044983, 0.8981751799583435, 0.975591778755188, 0.8067836761474609, 1.3518435955047607, 0.6573025584220886, 1.0304802656173706, 1.6685503721237183, 1.0553526878356934, 0.5711097121238708, 1.0247009992599487, 0.6176876425743103, 1.016655445098877, 0.982247531414032, 1.0350502729415894, 1.2114248275756836, 0.9113568067550659, 0.8153950572013855, 0.8797852396965027, 1.0338380336761475, 1.116428017616272, 1.1201506853103638, 0.8609657287597656, 0.912676215171814, 1.710379958152771, 1.090474009513855, 0.8915513157844543, 1.1894944906234741, 0.8708115816116333, 1.0665690898895264, 1.0305169820785522, 0.5747047066688538, 1.1592063903808594, 0.946173369884491, 0.8351022005081177, 1.5596749782562256, 1.6849561929702759, 0.7636805772781372, 1.4751542806625366, 0.9482348561286926, 0.704127311706543, 1.14241623878479, 0.3822685778141022, 0.838700532913208, 1.1125234365463257, 1.0268292427062988, 1.6789398193359375, 1.0846689939498901, 0.8588587045669556, 1.0380655527114868, 1.1836472749710083, 0.8935012817382812, 0.7408683896064758, 1.5573409795761108, 1.5664467811584473, 0.6777783632278442, 1.1856201887130737, 0.7630326747894287, 0.8157008290290833, 1.3681749105453491, 1.5858796834945679, 0.8068116307258606, 1.046944499015808, 0.6208876371383667, 0.9230483174324036, 0.8363816142082214, 1.104596495628357, 1.1330193281173706, 1.1311640739440918, 1.0731570720672607, 1.0417006015777588, 0.796082615852356, 0.9921092987060547, 1.0821648836135864, 1.1055179834365845, 1.0036746263504028, 1.0076035261154175, 0.8352872133255005, 0.930535078048706, 0.8846325278282166, 0.5116803646087646, 1.2088197469711304, 0.7404813766479492, 0.7430851459503174, 1.3486343622207642, 0.9051328897476196, 1.2491974830627441, 0.8088068962097168, 0.8904019594192505, 0.6812413930892944, 1.213348627090454, 0.8768427968025208, 2.1285393238067627, 1.2039724588394165, 0.9548261761665344, 1.2420108318328857, 1.0576876401901245, 1.0470387935638428, 1.0547642707824707, 0.8824198246002197, 1.0281121730804443, 0.8804724812507629, 1.5402249097824097, 1.0094337463378906, 0.6283329725265503, 1.0371050834655762, 1.1402766704559326, 0.7430152893066406, 0.7750612497329712, 1.181553602218628, 0.9303561449050903, 1.171072244644165, 0.8537359237670898, 0.5575534105300903, 1.0297635793685913, 1.038361668586731, 0.7867982983589172, 1.2124546766281128, 1.3936039209365845, 0.9233094453811646, 0.6561165452003479, 1.0920101404190063, 0.906432032585144, 0.9294338822364807, 1.7856104373931885, 0.93808513879776, 1.3832931518554688, 30.24072265625, 56.7115478515625, 44.635467529296875, 14.761631965637207, 62.16701889038086, 133.58370971679688, 67.26811981201172, 106.9583969116211, 27.19443702697754, 131.19464111328125, 57.1634521484375, 27.89203643798828, 26.366546630859375, 56.12778854370117, 48.86305618286133, 88.07212829589844, 55.654541015625, 105.79715728759766, 71.11428833007812, 23.009613037109375, 75.52676391601562, 75.94097137451172, 125.12325286865234, 41.119686126708984, 14.701568603515625, 35.4576416015625, 56.3353271484375, 21.95147705078125, 36.05080795288086, 180.4298858642578, 106.436279296875, 80.38442993164062, 35.4168701171875, 18.08243179321289, 16.125274658203125, 32.60976791381836, 173.5587921142578, 61.8452262878418, 85.78325653076172, 106.5013427734375, 34.97307205200195, 36.65932846069336, 24.251953125, 18.899518966674805, 90.5027847290039, 46.93988037109375, 41.87407302856445, 108.87319946289062, 88.03136444091797, 103.76263427734375, 39.36586380004883, 91.0736083984375, 169.6083221435547, 32.497859954833984, 20.48409652709961, 85.428466796875, 109.92634582519531, 48.18722915649414, 27.11892318725586, 27.4617919921875, 33.40948486328125, 16.8438720703125, 18.107574462890625, 159.78335571289062, 117.05511474609375, 72.13679504394531, 105.13321685791016, 140.04344177246094, 53.21998977661133, 51.6425666809082, 170.2161865234375, 22.05804443359375, 73.19051361083984, 21.39766502380371, 176.70675659179688, 83.63784790039062, 28.49970817565918, 179.1189727783203, 46.46851348876953, 147.58401489257812, 119.72774505615234, 30.168107986450195, 118.20184326171875, 65.90046691894531, 57.016448974609375, 71.61482238769531, 63.30264663696289, 31.01161003112793, 22.92497444152832, 30.030668258666992, 93.18485260009766, 154.797119140625, 44.75400924682617, 121.608154296875, 18.30145263671875, 58.351776123046875, 44.45557403564453, 88.06554412841797, 112.123779296875, 131.605224609375, 27.88165283203125, 77.80465698242188, 72.38470458984375, 109.5334243774414, 32.75579833984375, 67.8299560546875, 61.12337875366211, 21.478702545166016, 89.3388671875, 30.568077087402344, 24.39044189453125, 47.27393341064453, 81.08062744140625, 18.01194953918457, 20.8148193359375, 90.92349243164062, 63.77632522583008, 86.39017486572266, 73.651611328125, 48.689544677734375, 50.39236068725586, 72.4698486328125, 36.22021484375, 114.58927154541016, 60.90725326538086, 93.9421157836914, 102.27091217041016, 37.44390869140625, 61.563114166259766, 36.1512451171875, 57.160888671875, 145.9178924560547, 70.1190185546875, 138.78065490722656, 114.49262237548828, 47.49126052856445, 46.82525634765625, 136.44000244140625, 57.41828155517578, 80.73833465576172, 161.49826049804688, 158.07730102539062, 54.75283432006836, 51.62225341796875, 28.69964599609375, 45.70791244506836, 16.390960693359375, 22.170961380004883, 65.90882873535156, 58.220760345458984, 65.82181549072266, 117.2223892211914, 67.4979248046875, 52.15185546875, 25.471561431884766, 88.72677612304688, 37.3415412902832, 19.146278381347656, 63.883514404296875, 59.425048828125, 184.30101013183594, 118.16851043701172, 69.90819549560547, 86.52843475341797, 26.67425537109375, 20.70718002319336, 37.16790771484375, 33.65717315673828, 67.10629272460938, 43.09357452392578, 71.02104949951172, 27.279027938842773, 41.80753707885742, 97.1683349609375, 20.35162353515625, 57.565277099609375, 116.6988525390625, 35.67766189575195, 188.76773071289062, 36.955345153808594, 39.481388092041016, 37.66667938232422, 56.285457611083984, 39.04239273071289, 63.84903335571289, 63.95353698730469, 34.050907135009766, 31.918607711791992, 72.6768798828125, 59.24114990234375, 30.617401123046875, 21.112152099609375, 27.856796264648438, 93.11876678466797, 138.85821533203125, 63.391204833984375, 57.341312408447266, 40.412933349609375, 109.46478271484375, 146.50259399414062, 70.767333984375, 29.892324447631836, 110.66815948486328, 207.0449981689453, 49.69480514526367, 56.1603889465332, 22.037660598754883, 82.88927459716797, 75.92497253417969, 83.4017562866211, 103.52257537841797, 120.71402740478516, 29.50470542907715, 88.49320220947266, 50.338191986083984, 35.89530563354492, 19.96830940246582, 66.97721099853516, 60.2791748046875, 33.27884292602539, 69.71903991699219, 111.99662017822266, 106.94445037841797, 106.63394165039062, 27.16204833984375, 36.60264587402344, 36.940189361572266, 93.00968170166016, 41.46082305908203, 36.45137023925781, 27.95843505859375, 105.58273315429688, 26.563405990600586, 152.4578857421875, 50.172157287597656, 102.99571990966797, 29.297908782958984, 76.61492156982422, 88.7322769165039, 125.13462829589844, 107.28585815429688, 23.314481735229492, 135.59136962890625, 14.314239501953125, 62.2451286315918, 52.07660675048828, 46.226112365722656, 39.24169921875, 149.67108154296875, 46.21527099609375, 28.82503318786621, 53.22561264038086, 39.71405029296875, 140.03140258789062, 186.9401397705078, 127.1308364868164, 102.5262680053711, 32.39141845703125, 39.87811279296875, 36.09356689453125, 35.56141662597656, 27.50303077697754, 78.36396026611328, 70.65719604492188, 83.15015411376953, 155.4754638671875, 50.86419677734375, 212.3086700439453, 19.77362060546875, 125.30382537841797, 70.93661499023438, 50.37826919555664, 150.5575408935547, 17.34490203857422, 135.98240661621094, 115.0370864868164, 108.48318481445312, 21.091644287109375, 16.030702590942383, 119.07474517822266, 52.095027923583984, 91.4209976196289, 97.70560455322266, 78.64002990722656, 90.04499053955078, 37.53855895996094, 174.6392364501953, 38.85480880737305, 65.8584976196289, 38.09247589111328, 39.56740951538086, 63.415771484375, 61.48644256591797, 92.69264221191406, 75.71438598632812, 30.50439453125, 147.538818359375, 157.61209106445312, 26.346435546875, 100.40594482421875, 3.1447649002075195, 2.915696859359741, 3.093620538711548, 2.0005600452423096, 2.308692693710327, 1.523490309715271, 2.641139268875122, 1.7162050008773804, 1.833993673324585, 2.8108086585998535, 1.657120943069458, 1.2494465112686157, 2.3963279724121094, 1.8003596067428589, 1.5892597436904907, 2.4370927810668945, 1.4067507982254028, 2.99749755859375, 1.6089239120483398, 2.4358346462249756, 1.903895378112793, 2.017205238342285, 3.008052110671997, 2.925978422164917, 2.906275510787964, 2.2896623611450195, 2.3335044384002686, 2.2589683532714844, 2.9670958518981934, 3.065687894821167, 2.1861212253570557, 2.301215648651123, 2.2282018661499023, 2.291531562805176, 2.857659339904785, 2.7206640243530273, 1.7297054529190063, 1.5320913791656494, 3.808821439743042, 3.513035774230957, 1.5338066816329956, 1.7103344202041626, 1.7222145795822144, 2.3749682903289795, 2.166285514831543, 4.199636936187744, 1.7605353593826294, 1.6443787813186646, 1.4531296491622925, 2.553866147994995, 2.575726270675659, 2.0408430099487305, 1.7975624799728394, 1.4606331586837769, 1.4537895917892456, 1.8229856491088867, 1.210519790649414, 2.749568462371826, 1.8847283124923706, 2.8317995071411133, 1.7175228595733643, 2.1216630935668945, 3.695542573928833, 2.1350889205932617, 2.1315317153930664, 2.6330840587615967, 2.9811782836914062, 1.8731261491775513, 1.2967499494552612, 1.5498498678207397, 2.933189630508423, 2.893152952194214, 3.187384605407715, 3.433112144470215, 2.751962184906006, 2.5058794021606445, 2.7281811237335205, 2.807347297668457, 1.7381166219711304, 1.36393404006958, 2.1649580001831055, 1.8570318222045898, 2.642918586730957, 2.3268344402313232, 1.8066130876541138, 2.376274585723877, 1.2267999649047852, 1.3614815473556519, 2.258527994155884, 1.7975655794143677, 2.155867576599121, 1.5512572526931763, 2.9398765563964844, 1.8009328842163086, 2.0723071098327637, 3.003648042678833, 1.803175926208496, 2.468442440032959, 2.073451280593872, 3.5706357955932617, 1.3711919784545898, 3.566558837890625, 1.8190107345581055, 2.3873698711395264, 2.417616844177246, 2.5906004905700684, 2.8311550617218018, 2.832005500793457, 2.454465627670288, 2.453202247619629, 2.431203842163086, 1.8891477584838867, 2.1421289443969727, 3.588900566101074, 2.894213914871216, 1.256711721420288, 1.421793818473816, 2.4649438858032227, 2.495722770690918, 1.4717110395431519, 1.494947075843811, 1.4900546073913574, 2.033822536468506, 2.2561521530151367, 2.333500862121582, 1.2033135890960693, 2.2338109016418457, 3.0110924243927, 1.7525410652160645, 2.0327863693237305, 2.325835943222046, 2.522672176361084, 1.0897512435913086, 2.207016944885254, 1.9375131130218506, 1.5010290145874023, 1.8646057844161987, 2.193288564682007, 2.451441526412964, 1.8784722089767456, 1.3162811994552612, 2.5038843154907227, 2.7931888103485107, 2.0569169521331787, 2.8674633502960205, 2.8398690223693848, 2.5016298294067383, 2.89626407623291, 2.1143600940704346, 2.9262497425079346, 3.329861640930176, 2.000150680541992, 2.792140245437622, 1.8979253768920898, 1.5521879196166992, 1.8480232954025269, 2.561328411102295, 2.236443281173706, 2.5263986587524414, 1.3338056802749634, 1.4003782272338867, 1.9620475769042969, 2.3407466411590576, 1.9854763746261597, 2.6382713317871094, 2.743748664855957, 1.9328151941299438, 2.185868978500366, 1.589996099472046, 1.7780685424804688, 2.6414153575897217, 2.371853828430176, 2.2947425842285156, 1.3040804862976074, 2.410581111907959, 1.9715490341186523, 1.9920166730880737, 2.376845359802246, 2.124213218688965, 1.7495718002319336, 1.6087760925292969, 2.394343376159668, 2.5453827381134033, 1.7319515943527222, 2.4269607067108154, 2.825099229812622, 1.857304334640503, 1.753447413444519, 2.3400890827178955, 2.1855432987213135, 1.5345242023468018, 2.048874855041504, 2.518386125564575, 1.2220487594604492, 2.525090217590332, 2.569014549255371, 1.6740151643753052, 2.9136204719543457, 2.11620831489563, 1.8058544397354126, 2.931584358215332, 1.7841887474060059, 2.586270809173584, 2.3345041275024414, 2.533240556716919, 3.2171623706817627, 1.7664178609848022, 2.156100273132324, 2.070651054382324, 1.9776948690414429, 2.352421760559082, 2.9634032249450684, 1.8187551498413086, 1.9679843187332153, 1.7641574144363403, 1.7592781782150269, 2.1936471462249756, 2.061905860900879, 1.3871773481369019, 3.3208723068237305, 3.9588229656219482, 1.4211128950119019, 1.7351272106170654, 2.242764472961426, 2.167361259460449, 1.9503147602081299, 2.9553463459014893, 1.807145357131958, 3.6557705402374268, 1.6085455417633057, 2.190479040145874, 1.9171496629714966, 1.0773191452026367, 1.9492778778076172, 3.1170244216918945, 2.437976360321045, 3.252396583557129, 2.4519948959350586, 1.5204704999923706, 1.9716218709945679, 2.154650926589966, 2.832627773284912, 1.6299314498901367, 1.785954236984253, 2.117328405380249, 1.8010892868041992, 2.129558563232422, 2.8768742084503174, 1.393576979637146, 0.8233503699302673, 2.22818660736084, 2.759394884109497, 2.6062610149383545, 2.6123459339141846, 1.6734952926635742, 3.3890292644500732, 2.1500496864318848, 2.453090190887451, 3.2307538986206055, 2.5426511764526367, 1.6539963483810425, 2.8370769023895264, 1.8294308185577393, 1.4764236211776733, 2.4331650733947754, 2.198267936706543, 2.202481269836426, 2.667841672897339, 3.1018402576446533, 1.5311641693115234, 2.016900062561035, 2.068495512008667, 3.3951079845428467, 3.187108039855957, 2.4632692337036133, 1.277485728263855, 2.463131904602051, 1.7175321578979492, 2.175199270248413, 2.3905858993530273, 1.747488021850586, 2.4015207290649414, 2.102475166320801, 2.5139524936676025, 1.806225061416626, 1.9965258836746216, 2.6823036670684814, 3.148787260055542, 1.6080235242843628, 2.318347692489624, 2.6517248153686523, 2.950608491897583, 1.96773099899292, 2.039794683456421, 2.687901496887207, 2.252236843109131, 2.4666261672973633, 2.541964530944824, 2.5529050827026367, 3.275311231613159, 0.07689182460308075, 0.18709631264209747, 0.18995347619056702, 0.13426423072814941, 0.1757689267396927, 0.11482824385166168, 0.1352459043264389, 0.14722847938537598, 0.14210925996303558, 0.17600710690021515, 0.13801440596580505, 0.15833128988742828, 0.1432715356349945, 0.09089362621307373, 0.17420756816864014, 0.09490181505680084, 0.1545279622077942, 0.13656826317310333, 0.20857422053813934, 0.2096695899963379, 0.08426458388566971, 0.14863751828670502, 0.13335010409355164, 0.11967483162879944, 0.1606380045413971, 0.05938626080751419, 0.18928122520446777, 0.15594002604484558, 0.15225738286972046, 0.2075245976448059, 0.127924844622612, 0.06943803280591965, 0.15624409914016724, 0.15511083602905273, 0.11558465659618378, 0.18813668191432953, 0.17053072154521942, 0.2019176483154297, 0.11124151200056076, 0.16314800083637238, 0.08614778518676758, 0.10148542374372482, 0.2033863365650177, 0.106317438185215, 0.12771648168563843, 0.1552451103925705, 0.15195061266422272, 0.1238335371017456, 0.1896073818206787, 0.12927746772766113, 0.11330312490463257, 0.1110047772526741, 0.1459696888923645, 0.16797204315662384, 0.09151918441057205, 0.1843341439962387, 0.14308421313762665, 0.07683844119310379, 0.132626011967659, 0.11596091091632843, 0.14335349202156067, 0.15627223253250122, 0.16691851615905762, 0.1521034985780716, 0.15492476522922516, 0.05494095757603645, 0.19716854393482208, 0.18372967839241028, 0.15394878387451172, 0.09493394941091537, 0.178034707903862, 0.07942427694797516, 0.1855824589729309, 0.14966490864753723, 0.07052591443061829, 0.12653861939907074, 0.1416458934545517, 0.1263171285390854, 0.15017849206924438, 0.18603362143039703, 0.10801246762275696, 0.18210048973560333, 0.11842665076255798, 0.0583328939974308, 0.14267443120479584, 0.13340097665786743, 0.03952375799417496, 0.14980660378932953, 0.1657513827085495, 0.1523856371641159, 0.20055623352527618, 0.10967705398797989, 0.0808548703789711, 0.10135896503925323, 0.12504424154758453, 0.1552886962890625, 0.1470550298690796, 0.11807429790496826, 0.08394404500722885, 0.07458589226007462, 0.1884213536977768, 0.13175469636917114, 0.08614823967218399, 0.13201415538787842, 0.1275632679462433, 0.12491243332624435, 0.14720530807971954, 0.0665971040725708, 0.06875546276569366, 0.09733930975198746, 0.15617568790912628, 0.08341516554355621, 0.19212670624256134, 0.16545744240283966, 0.1492023766040802, 0.06731820851564407, 0.14985325932502747, 0.061546094715595245, 0.10465189814567566, 0.10763871669769287, 0.12346352636814117, 0.10067439079284668, 0.1280406415462494, 0.16749641299247742, 0.14081446826457977, 0.182281032204628, 0.14472949504852295, 0.13556914031505585, 0.18206043541431427, 0.1141132041811943, 0.13537855446338654, 0.20721904933452606, 0.08224992454051971, 0.12593907117843628, 0.21187667548656464, 0.2124968320131302, 0.16994509100914001, 0.1282801628112793, 0.17467422783374786, 0.17269141972064972, 0.15003518760204315, 0.10719810426235199, 0.10432504117488861, 0.09562177211046219, 0.11390220373868942, 0.14420640468597412, 0.19352580606937408, 0.1399003118276596, 0.18256722390651703, 0.1982133388519287, 0.09045207500457764, 0.16858713328838348, 0.1313028335571289, 0.072182297706604, 0.14460605382919312, 0.16160856187343597, 0.11253129690885544, 0.09087546914815903, 0.0841541439294815, 0.20504321157932281, 0.08351293206214905, 0.13970589637756348, 0.15100644528865814, 0.09624128043651581, 0.09016960859298706, 0.18287873268127441, 0.1868124008178711, 0.10338588804006577, 0.14216232299804688, 0.1567053496837616, 0.13083451986312866, 0.14223237335681915, 0.10579998046159744, 0.07136242836713791, 0.09780316799879074, 0.16107411682605743, 0.10374651849269867, 0.12613005936145782, 0.14709973335266113, 0.17560243606567383, 0.14564098417758942, 0.08782924711704254, 0.17078781127929688, 0.1810440570116043, 0.13492824137210846, 0.14330588281154633, 0.10931147634983063, 0.10219889134168625, 0.1308954954147339, 0.13438552618026733, 0.1284051090478897, 0.08600513637065887, 0.2009495049715042, 0.10445499420166016, 0.16662079095840454, 0.14012587070465088, 0.17851205170154572, 0.17068034410476685, 0.15292979776859283, 0.1402512937784195, 0.1555625945329666, 0.06336987018585205, 0.14997826516628265, 0.13165980577468872, 0.05531250312924385, 0.14892072975635529, 0.12621217966079712, 0.12619416415691376, 0.1219124123454094, 0.14027415215969086, 0.16105090081691742, 0.0963774099946022, 0.1272060126066208, 0.09864909946918488, 0.1605285406112671, 0.1505708545446396, 0.13458573818206787, 0.17393946647644043, 0.15474055707454681, 0.07764498889446259, 0.06191800907254219, 0.13557493686676025, 0.1312178522348404, 0.17924338579177856, 0.10799932479858398, 0.12605440616607666, 0.15524369478225708, 0.1692742109298706, 0.1420358419418335, 0.0896277204155922, 0.18294212222099304, 0.12923508882522583, 0.14652349054813385, 0.09017906337976456, 0.10570373386144638, 0.17408517003059387, 0.1321244090795517, 0.16962558031082153, 0.11197040230035782, 0.16235585510730743, 0.1180904358625412, 0.16804878413677216, 0.12447156757116318, 0.144872784614563, 0.16207973659038544, 0.12222474813461304, 0.09315191209316254, 0.158834308385849, 0.11185484379529953, 0.08549322187900543, 0.12886784970760345, 0.11872442066669464, 0.11924829334020615, 0.14007169008255005, 0.18724803626537323, 0.13942813873291016, 0.12822118401527405, 0.1488361358642578, 0.18791553378105164, 0.07877887785434723, 0.07649266719818115, 0.11071881651878357, 0.11039861291646957, 0.16134418547153473, 0.17079395055770874, 0.09518381208181381, 0.17515578866004944, 0.10319626331329346, 0.1453435719013214, 0.1673501580953598, 0.12393619120121002, 0.16125933825969696, 0.14293883740901947, 0.10593967139720917, 0.14145642518997192, 0.09340248256921768, 0.13298752903938293, 0.11745746433734894, 0.12783260643482208, 0.11375880986452103, 0.17352357506752014, 0.19135797023773193, 0.13790273666381836, 0.12044938653707504, 0.11669943481683731, 0.14307191967964172, 0.08601956814527512, 0.11579041928052902, 0.22274012863636017, 0.047674670815467834, 0.144034281373024, 0.15073323249816895, 0.1884811371564865, 0.1060674712061882, 0.16755004227161407, 0.19186125695705414, 0.16996867954730988, 0.13419200479984283, 0.16504473984241486, 0.09959101676940918, 0.7349554300308228, 1.0887000560760498, 1.151350975036621, 1.696203589439392, 1.3616602420806885, 1.0492784976959229, 0.651528000831604, 1.1428470611572266, 0.7724892497062683, 0.7603676915168762, 1.468975305557251, 1.1278867721557617, 1.3570057153701782, 0.923183262348175, 1.3783336877822876, 0.7548487782478333, 1.412517786026001, 1.0589625835418701, 1.2256442308425903, 1.4296795129776, 0.8055184483528137, 0.6049732565879822, 1.1329121589660645, 0.7062972187995911, 0.9933797717094421, 0.7575969696044922, 0.5078877806663513, 1.196557641029358, 1.255595326423645, 0.49359893798828125, 1.0620403289794922, 0.8078658580780029, 1.2048895359039307, 1.1385507583618164, 0.9278231859207153, 0.5115165710449219, 0.9014596343040466, 0.7452055215835571, 1.4392800331115723, 0.9978558421134949, 0.5558935403823853, 0.43961355090141296, 0.6126516461372375, 1.1875560283660889, 1.0718069076538086, 0.7910671234130859, 1.1072534322738647, 1.0366719961166382, 0.8430268168449402, 0.9483550190925598, 1.18613600730896, 0.7601290941238403, 1.2026500701904297, 1.0909655094146729, 1.3731510639190674, 1.0553520917892456, 0.35646095871925354, 0.656821608543396, 1.4819021224975586, 0.9403325319290161, 0.7896851897239685, 0.8057020306587219, 0.74563068151474, 1.0446678400039673, 0.9192677736282349, 0.4979609549045563, 0.9704834818840027, 1.6265146732330322, 1.2680952548980713, 1.3017127513885498, 0.9791086316108704, 0.6002200841903687, 1.0329418182373047, 0.6203293204307556, 1.2022314071655273, 0.775462806224823, 0.9528836011886597, 0.76485675573349, 0.8836650848388672, 0.5889171957969666, 1.1369996070861816, 1.3947187662124634, 0.9493006467819214, 1.4459940195083618, 0.7249236106872559, 0.8055120706558228, 1.5120928287506104, 0.8689308166503906, 1.020608901977539, 1.226869821548462, 0.8726680278778076, 1.3115355968475342, 1.2285363674163818, 1.5965074300765991, 0.8117907643318176, 1.3474409580230713, 1.0533795356750488, 1.0379341840744019, 0.7756190299987793, 1.302762746810913, 0.5033184885978699, 0.6963462829589844, 1.427376627922058, 1.2012479305267334, 0.633834719657898, 1.1878706216812134, 1.894389271736145, 0.975372314453125, 0.6832131743431091, 1.0958762168884277, 0.8156904578208923, 1.0393168926239014, 1.4328734874725342, 1.0487046241760254, 0.8874946236610413, 1.617706298828125, 0.9480955004692078, 0.8761793375015259, 1.3932198286056519, 0.8961146473884583, 0.8379482626914978, 1.360845923423767, 0.8410569429397583, 1.385454535484314, 0.9109677076339722, 1.3016331195831299, 1.1638507843017578, 0.5100476741790771, 0.4775579869747162, 1.2151470184326172, 1.0016937255859375, 1.477826476097107, 0.9977418184280396, 0.9058305025100708, 1.1117364168167114, 1.2027075290679932, 1.3972370624542236, 1.6688135862350464, 1.1157413721084595, 1.2922580242156982, 0.4473344385623932, 0.9249905347824097, 0.7941930890083313, 0.4825343191623688, 1.2482891082763672, 1.054179310798645, 0.781482994556427, 0.8203870058059692, 0.7145892381668091, 0.9156411290168762, 0.791424572467804, 1.725855827331543, 0.8765047192573547, 1.1657567024230957, 0.9766217470169067, 1.1260403394699097, 0.925004780292511, 1.1562633514404297, 0.7729487419128418, 1.134225845336914, 0.6399539113044739, 0.9483717083930969, 1.3628345727920532, 0.5712050795555115, 0.8899356126785278, 1.0218572616577148, 1.0717519521713257, 0.38964980840682983, 1.5461965799331665, 1.349285364151001, 1.5071625709533691, 0.6531599164009094, 1.1666009426116943, 1.1180105209350586, 1.157399296760559, 0.6214473247528076, 0.5111799240112305, 1.4685763120651245, 1.397790789604187, 1.282870888710022, 0.7738637924194336, 0.4690704345703125, 0.6694234609603882, 0.4698934555053711, 1.1720893383026123, 1.0402485132217407, 1.1545144319534302, 1.1220589876174927, 1.1703821420669556, 0.813984215259552, 0.7632196545600891, 0.9829017519950867, 1.4171862602233887, 0.544154942035675, 0.8368967175483704, 1.4544645547866821, 1.7872402667999268, 0.8466053009033203, 0.8712812662124634, 0.47108206152915955, 1.3200712203979492, 0.8605279326438904, 1.0031743049621582, 1.4686554670333862, 1.7637494802474976, 1.0411388874053955, 0.6634904146194458, 1.0668621063232422, 0.8089426755905151, 1.389873743057251, 1.4612575769424438, 0.7351823449134827, 0.6726829409599304, 1.1943533420562744, 1.3300448656082153, 0.6292381286621094, 1.1989519596099854, 0.9172778129577637, 0.7353639006614685, 0.7964088320732117, 0.840399444103241, 0.8504357933998108, 1.0881931781768799, 1.0270869731903076, 0.6804197430610657, 0.9742247462272644, 1.5801101922988892, 0.744110107421875, 0.8804023265838623, 1.1936745643615723, 1.3488954305648804, 0.9713665843009949, 0.7541405558586121, 1.972137451171875, 0.551372230052948, 0.6890961527824402, 0.841614842414856, 1.4245449304580688, 0.7219918370246887, 1.044692039489746, 1.1341273784637451, 1.110601782798767, 1.429986834526062, 0.9585661292076111, 0.8137115836143494, 0.5866707563400269, 0.8633415102958679, 1.2270104885101318, 0.8187519907951355, 1.7411596775054932, 0.7894757390022278, 0.8698809742927551, 0.9089792370796204, 0.6446628570556641, 0.546815037727356, 0.7768056988716125, 1.4818590879440308, 1.4085613489151, 0.7674664258956909, 0.8715314865112305, 0.9468259811401367, 1.2423969507217407, 0.9187003970146179, 1.0469814538955688, 1.1402968168258667, 0.854897141456604, 0.7847493290901184, 1.0482758283615112, 1.3255642652511597, 0.862514317035675, 0.9643465280532837, 1.0247794389724731, 1.2188441753387451, 1.1967405080795288, 0.6674330830574036, 1.2538825273513794, 1.1409645080566406, 1.076723337173462, 1.4276946783065796, 1.2644952535629272, 1.1188251972198486, 0.8476659059524536, 0.9448171854019165, 0.7717899680137634, 0.8620967864990234, 1.1849122047424316, 0.877754807472229, 0.6544540524482727, 0.9814919829368591, 1.1233781576156616, 1.0975608825683594, 1.1748954057693481, 0.8897116780281067, 1.6089662313461304, 1.4060372114181519, 0.9341301321983337, 1.1034959554672241, 1.1149619817733765, 0.6299821138381958, 0.4678899347782135, 27.78146743774414, 19.002960205078125, 21.54400634765625, 27.96240234375, 76.41221618652344, 56.180633544921875, 48.50677490234375, 34.700565338134766, 71.4727783203125, 70.66622924804688, 33.06507873535156, 75.78634643554688, 96.07498168945312, 28.76776123046875, 17.68233299255371, 112.03070068359375, 66.525390625, 18.9652099609375, 173.83946228027344, 148.73988342285156, 86.77812194824219, 101.05398559570312, 83.46540832519531, 64.2211685180664, 29.911211013793945, 23.33203125, 24.94111442565918, 56.5518798828125, 42.265869140625, 87.08263397216797, 28.5035400390625, 40.73724365234375, 33.46209716796875, 141.09642028808594, 26.43458366394043, 51.38772201538086, 19.845184326171875, 80.97901916503906, 63.880916595458984, 17.54803466796875, 91.3682861328125, 98.95536041259766, 57.24576187133789, 49.442195892333984, 67.98639678955078, 19.55987548828125, 136.02713012695312, 23.45143699645996, 147.25592041015625, 51.867591857910156, 23.550321578979492, 87.63794708251953, 244.7069091796875, 20.079742431640625, 137.14678955078125, 21.741024017333984, 98.98797607421875, 99.323486328125, 181.9668731689453, 37.96721649169922, 64.83926391601562, 116.89315795898438, 75.10456848144531, 131.0404052734375, 117.87458801269531, 22.622953414916992, 78.5753402709961, 107.78011322021484, 29.856510162353516, 55.07763671875, 79.03398895263672, 110.51744079589844, 121.40199279785156, 50.18413162231445, 93.83294677734375, 114.6230239868164, 19.262298583984375, 86.94720458984375, 53.00750732421875, 33.23663330078125, 76.57321166992188, 58.4578857421875, 13.07414722442627, 25.377899169921875, 36.00849533081055, 51.70064163208008, 55.02561569213867, 28.350341796875, 84.6995849609375, 106.27788543701172, 27.238554000854492, 117.39364624023438, 16.285125732421875, 33.569454193115234, 60.6090087890625, 70.76006317138672, 68.72750854492188, 51.8262939453125, 36.025386810302734, 122.4969482421875, 128.15023803710938, 133.527587890625, 119.99267578125, 24.4136962890625, 63.783660888671875, 65.522705078125, 114.65667724609375, 152.27059936523438, 78.73957061767578, 19.996063232421875, 137.92752075195312, 145.39659118652344, 62.46670150756836, 172.8017120361328, 48.8157958984375, 55.931888580322266, 26.219858169555664, 66.98685455322266, 30.06390380859375, 13.36339282989502, 21.28662109375, 25.382587432861328, 133.0596466064453, 62.21722412109375, 32.99514389038086, 108.26576232910156, 127.6898193359375, 14.070526123046875, 119.55462646484375, 78.47451782226562, 45.04872131347656, 22.39234733581543, 76.82060241699219, 55.96430587768555, 22.3817138671875, 37.104339599609375, 129.90975952148438, 97.03079986572266, 22.35888671875, 21.354413986206055, 31.800296783447266, 57.28601837158203, 47.4710693359375, 36.45989990234375, 121.25531005859375, 21.69915771484375, 62.28839874267578, 63.16679382324219, 90.97296905517578, 84.96589660644531, 39.97515869140625, 43.31654357910156, 138.96755981445312, 13.989351272583008, 100.7243423461914, 112.2880859375, 64.4193344116211, 116.44692993164062, 36.24429702758789, 70.1999282836914, 17.916475296020508, 100.42925262451172, 108.99945831298828, 57.91744613647461, 92.788818359375, 108.24492645263672, 29.73687744140625, 74.47418212890625, 22.771766662597656, 19.51727294921875, 46.40431594848633, 20.04364776611328, 146.20712280273438, 91.91365051269531, 166.454833984375, 84.1552505493164, 108.7034912109375, 53.5795783996582, 73.00637817382812, 90.25003814697266, 123.4935531616211, 57.08277130126953, 68.95327758789062, 162.7921905517578, 96.44033813476562, 19.3536376953125, 17.904354095458984, 114.11126708984375, 128.95928955078125, 138.46051025390625, 115.334228515625, 27.387357711791992, 38.97471237182617, 90.90351104736328, 88.0223388671875, 90.41109466552734, 59.274139404296875, 194.37548828125, 20.03680419921875, 30.348876953125, 80.65692138671875, 31.95973014831543, 86.54548645019531, 105.40897369384766, 55.49498748779297, 170.4339599609375, 66.98455810546875, 107.7530517578125, 27.083984375, 30.108673095703125, 60.961761474609375, 31.748458862304688, 46.67041015625, 131.12701416015625, 41.669647216796875, 80.87798309326172, 65.90106964111328, 45.60451889038086, 114.84989166259766, 26.604557037353516, 62.2083740234375, 24.558998107910156, 75.9051513671875, 43.23488235473633, 36.88018798828125, 168.85110473632812, 112.41605377197266, 32.753238677978516, 71.47246551513672, 77.76762390136719, 66.42876434326172, 83.62747955322266, 129.86776733398438, 46.9124755859375, 45.31045913696289, 132.31890869140625, 149.6317138671875, 19.563873291015625, 58.606658935546875, 61.10904312133789, 65.1385498046875, 66.88894653320312, 50.43415069580078, 66.29525756835938, 24.2452392578125, 75.09860229492188, 121.19486236572266, 33.82904052734375, 46.9586181640625, 50.92655563354492, 81.8931884765625, 167.26210021972656, 77.40408325195312, 89.70568084716797, 119.17677307128906, 110.781005859375, 87.91240692138672, 172.0762481689453, 81.25655364990234, 104.84435272216797, 96.43017578125, 137.61033630371094, 37.87929916381836, 22.462860107421875, 101.53241729736328, 25.421321868896484, 47.97256851196289, 188.10205078125, 24.320341110229492, 17.25204849243164, 86.45684051513672, 102.0784912109375, 110.280029296875, 61.34320068359375, 75.123046875, 142.50401306152344, 29.592069625854492, 65.16580963134766, 32.27791976928711, 52.34700393676758, 107.728759765625, 48.42353820800781, 57.020076751708984, 85.26445770263672, 33.29093551635742, 87.74302673339844, 62.37343978881836, 66.52964782714844, 109.093505859375, 17.48809814453125, 78.68900299072266, 20.356536865234375, 58.93650436401367, 40.68145751953125, 75.36759948730469, 145.00225830078125, 259.7262878417969, 24.208280563354492, 25.1085205078125, 82.1429443359375, 1.8719619512557983, 2.5732672214508057, 3.0144708156585693, 1.4648536443710327, 3.5446746349334717, 2.805049419403076, 1.4736720323562622, 2.2737112045288086, 1.8816195726394653, 1.6694878339767456, 1.9435491561889648, 2.227323055267334, 2.6188385486602783, 3.9285130500793457, 2.405186414718628, 3.107086181640625, 2.4808642864227295, 2.065669059753418, 2.2026708126068115, 2.265420913696289, 2.1523702144622803, 3.107916831970215, 2.9933559894561768, 2.3332817554473877, 1.7853963375091553, 2.8713161945343018, 2.0456228256225586, 1.8385261297225952, 2.917285680770874, 2.3309166431427, 3.171414613723755, 3.6107146739959717, 3.1891613006591797, 2.277501106262207, 2.9059536457061768, 1.9243497848510742, 1.3532896041870117, 2.8871965408325195, 2.9542782306671143, 1.290994644165039, 1.5400463342666626, 1.9701642990112305, 2.220184087753296, 3.4829070568084717, 2.043259620666504, 1.856007695198059, 2.8157079219818115, 2.9512486457824707, 1.6947497129440308, 2.3188414573669434, 3.5098752975463867, 1.7649956941604614, 1.5486990213394165, 2.7849526405334473, 3.193291664123535, 1.6739501953125, 2.006840705871582, 1.421938419342041, 1.8119288682937622, 2.0651397705078125, 1.5832122564315796, 1.3214958906173706, 2.685382127761841, 2.6101481914520264, 2.3408470153808594, 1.2754188776016235, 1.1300508975982666, 1.6585400104522705, 2.400031089782715, 2.84836483001709, 2.187127113342285, 1.065608263015747, 2.7524445056915283, 2.7375383377075195, 2.056854009628296, 3.5951311588287354, 2.097740650177002, 2.4148402214050293, 1.6373770236968994, 1.9112415313720703, 3.1476147174835205, 1.5759992599487305, 3.6108109951019287, 2.32861328125, 1.5812526941299438, 2.344742774963379, 1.8501354455947876, 2.763076066970825, 3.024146556854248, 2.345921516418457, 1.1420525312423706, 1.6123137474060059, 3.5236308574676514, 3.0022823810577393, 3.188053846359253, 1.401528239250183, 2.188830614089966, 2.286783456802368, 3.3732540607452393, 2.3411171436309814, 2.152146339416504, 1.8918808698654175, 1.9482752084732056, 1.8987178802490234, 1.9639205932617188, 2.5678985118865967, 3.5324504375457764, 2.7902116775512695, 3.231149911880493, 2.239553213119507, 1.7323273420333862, 1.6652698516845703, 2.0003652572631836, 1.2856402397155762, 2.484225273132324, 1.7126553058624268, 1.9830684661865234, 3.5689783096313477, 1.904653549194336, 2.6129965782165527, 3.019031524658203, 1.7110836505889893, 3.033034324645996, 2.1230592727661133, 2.182011127471924, 2.490349292755127, 1.763832926750183, 2.076197624206543, 1.8375451564788818, 2.528491497039795, 3.2209978103637695, 2.6217808723449707, 1.4619054794311523, 2.256819725036621, 1.904616355895996, 1.9820852279663086, 2.7459704875946045, 2.5930566787719727, 2.7589447498321533, 2.1585350036621094, 2.055368423461914, 2.4303700923919678, 2.099087715148926, 2.6275084018707275, 2.1746044158935547, 3.183283567428589, 3.4861180782318115, 2.136829376220703, 1.7078533172607422, 1.654875636100769, 2.7133917808532715, 3.4505298137664795, 1.5140854120254517, 3.4353413581848145, 2.8850719928741455, 3.204549789428711, 2.5893163681030273, 2.7852728366851807, 2.324833869934082, 1.691733717918396, 1.4055336713790894, 1.9434051513671875, 1.8979253768920898, 2.1713438034057617, 2.978184700012207, 1.0570954084396362, 3.448794364929199, 2.259248971939087, 2.960223913192749, 1.6928337812423706, 2.6929290294647217, 1.3681896924972534, 1.9145281314849854, 2.4100453853607178, 2.6329824924468994, 3.1581242084503174, 1.4326013326644897, 1.9146524667739868, 2.3027145862579346, 3.50308895111084, 1.613505244255066, 1.6997737884521484, 1.718209147453308, 2.4021849632263184, 1.8284869194030762, 1.8497356176376343, 1.4589571952819824, 2.029446601867676, 1.1031856536865234, 1.87742018699646, 2.0301198959350586, 2.3856685161590576, 1.4641674757003784, 2.7577197551727295, 2.3748254776000977, 2.5120537281036377, 1.938252329826355, 2.0116939544677734, 2.5508716106414795, 3.0272152423858643, 2.4237780570983887, 2.1333208084106445, 3.293063163757324, 2.275256395339966, 1.2020313739776611, 2.4180245399475098, 2.4743335247039795, 2.0659494400024414, 1.3236593008041382, 1.9090169668197632, 3.200526714324951, 2.1736161708831787, 1.8196457624435425, 1.9962817430496216, 3.095353364944458, 2.88356614112854, 1.7511109113693237, 2.6515722274780273, 2.3346457481384277, 1.490328073501587, 2.663773775100708, 1.930513858795166, 3.1951587200164795, 2.609492063522339, 2.260850429534912, 2.3604893684387207, 1.40414559841156, 2.270888328552246, 1.700187087059021, 1.479414939880371, 1.9602456092834473, 2.3192567825317383, 2.065237283706665, 2.042438268661499, 2.1571578979492188, 1.8729841709136963, 2.6387410163879395, 1.7264432907104492, 2.554511308670044, 1.8040990829467773, 2.452188491821289, 2.9373695850372314, 1.9682250022888184, 1.9943512678146362, 2.56540584564209, 1.7373849153518677, 2.1829850673675537, 1.4954943656921387, 1.7742033004760742, 2.937542676925659, 1.9246286153793335, 1.8425512313842773, 2.3350765705108643, 1.315855860710144, 3.2490017414093018, 2.9407854080200195, 2.9683563709259033, 2.5576088428497314, 2.157543182373047, 2.572321653366089, 1.8079155683517456, 2.8960087299346924, 3.5997555255889893, 2.6143999099731445, 2.0407052040100098, 2.834712505340576, 2.551802396774292, 2.340193748474121, 2.2495739459991455, 2.4748926162719727, 1.4856066703796387, 1.468050479888916, 2.908215284347534, 2.409193277359009, 1.6057723760604858, 2.98081111907959, 2.086422920227051, 1.8985527753829956, 2.8763720989227295, 2.6861908435821533, 2.9535906314849854, 2.6402604579925537, 2.21658992767334, 2.3449316024780273, 2.6412627696990967, 3.1226882934570312, 2.4881982803344727, 2.099437713623047, 2.584113121032715, 2.995999574661255, 1.967376947402954, 2.271179676055908, 2.199916124343872, 1.826069951057434, 1.6067900657653809, 2.3900249004364014, 3.5311784744262695, 1.694117546081543, 1.742870807647705, 3.104426145553589, 0.13866928219795227, 0.08088276535272598, 0.08367413282394409, 0.11701643466949463, 0.1216868981719017, 0.19841916859149933, 0.12958553433418274, 0.08064300566911697, 0.10891915112733841, 0.19585943222045898, 0.18583181500434875, 0.139491468667984, 0.1437212973833084, 0.15889504551887512, 0.11003565788269043, 0.13537807762622833, 0.1810571700334549, 0.13300785422325134, 0.20003722608089447, 0.17586524784564972, 0.1459222435951233, 0.19404292106628418, 0.11576223373413086, 0.1812635064125061, 0.15720434486865997, 0.1469447761774063, 0.1724143624305725, 0.08847720921039581, 0.1634637862443924, 0.1317577362060547, 0.08082714676856995, 0.13587000966072083, 0.1448008418083191, 0.12633636593818665, 0.1423506736755371, 0.12184417247772217, 0.14202620089054108, 0.1283826380968094, 0.12824252247810364, 0.15970224142074585, 0.1269647181034088, 0.09029750525951385, 0.10224929451942444, 0.17970149219036102, 0.12558092176914215, 0.1171688437461853, 0.12698371708393097, 0.2042117863893509, 0.09995073080062866, 0.12545181810855865, 0.1712024211883545, 0.10980100184679031, 0.09302224963903427, 0.17733657360076904, 0.14609235525131226, 0.21715191006660461, 0.20530711114406586, 0.08548018336296082, 0.09856411069631577, 0.1878727674484253, 0.16419413685798645, 0.14670181274414062, 0.14717327058315277, 0.08486991375684738, 0.12614114582538605, 0.1120566725730896, 0.20815829932689667, 0.1903466433286667, 0.14285853505134583, 0.14542825520038605, 0.23209784924983978, 0.1878964602947235, 0.13384723663330078, 0.12382209300994873, 0.16145578026771545, 0.1518971174955368, 0.15052565932273865, 0.1387384980916977, 0.11916828155517578, 0.12090730667114258, 0.12113361805677414, 0.17125418782234192, 0.1628764122724533, 0.13140125572681427, 0.19894035160541534, 0.10467533022165298, 0.1625341922044754, 0.18347612023353577, 0.08613940328359604, 0.18335700035095215, 0.12115016579627991, 0.18383772671222687, 0.10809898376464844, 0.09375929832458496, 0.10770672559738159, 0.1298215240240097, 0.11228799819946289, 0.12432479858398438, 0.12660375237464905, 0.13175715506076813, 0.1063503548502922, 0.12768732011318207, 0.11257288604974747, 0.12906265258789062, 0.1357678771018982, 0.05902737379074097, 0.12551353871822357, 0.18510138988494873, 0.16104847192764282, 0.08715933561325073, 0.11623046547174454, 0.09340988099575043, 0.13534320890903473, 0.12690173089504242, 0.185556560754776, 0.09098707884550095, 0.10525912791490555, 0.14042483270168304, 0.12955373525619507, 0.14746464788913727, 0.1529986411333084, 0.14548370242118835, 0.19350020587444305, 0.13708870112895966, 0.11967107653617859, 0.1540205478668213, 0.10454212129116058, 0.10077909380197525, 0.16080398857593536, 0.15932875871658325, 0.10737722367048264, 0.048154134303331375, 0.17047210037708282, 0.07942990213632584, 0.14808805286884308, 0.17677466571331024, 0.159128800034523, 0.14357447624206543, 0.15078523755073547, 0.05460541695356369, 0.1680769920349121, 0.14302825927734375, 0.15109571814537048, 0.07364858686923981, 0.09354297071695328, 0.1445319950580597, 0.1928328275680542, 0.19684207439422607, 0.15182754397392273, 0.13054263591766357, 0.1270393580198288, 0.0850619301199913, 0.20272481441497803, 0.13130715489387512, 0.07562168687582016, 0.1297544687986374, 0.17046891152858734, 0.1381990909576416, 0.09671853482723236, 0.1372937560081482, 0.17010314762592316, 0.1385415494441986, 0.15489257872104645, 0.1348535567522049, 0.09552408009767532, 0.1909848153591156, 0.144141286611557, 0.07970681041479111, 0.09706413000822067, 0.13069385290145874, 0.15076854825019836, 0.11413197219371796, 0.1727350950241089, 0.13678453862667084, 0.15371175110340118, 0.16849642992019653, 0.1432580053806305, 0.07978586107492447, 0.1411932110786438, 0.0895443707704544, 0.13661015033721924, 0.12113895267248154, 0.13245879113674164, 0.1379338800907135, 0.19724999368190765, 0.17321783304214478, 0.15812598168849945, 0.1354513317346573, 0.13162463903427124, 0.058833539485931396, 0.10775032639503479, 0.1735558658838272, 0.1226939782500267, 0.1400994509458542, 0.17975693941116333, 0.14030364155769348, 0.17079097032546997, 0.10806453227996826, 0.093839131295681, 0.11574044823646545, 0.14807282388210297, 0.18909406661987305, 0.12295052409172058, 0.15267446637153625, 0.17791076004505157, 0.1932186633348465, 0.1532551348209381, 0.24282102286815643, 0.1795796900987625, 0.22713477909564972, 0.20153366029262543, 0.11416608840227127, 0.1354050487279892, 0.13098828494548798, 0.2802027463912964, 0.10853748023509979, 0.13934946060180664, 0.14475861191749573, 0.1268603801727295, 0.10888852924108505, 0.16311763226985931, 0.161160409450531, 0.1623699963092804, 0.06928597390651703, 0.05657569691538811, 0.1511756032705307, 0.10349147766828537, 0.17081308364868164, 0.16004283726215363, 0.0882648229598999, 0.12192028015851974, 0.180190309882164, 0.13499613106250763, 0.17353364825248718, 0.11376883089542389, 0.1192452535033226, 0.2099866420030594, 0.1223764568567276, 0.20851464569568634, 0.1948022097349167, 0.14736169576644897, 0.11775436997413635, 0.12446039170026779, 0.09784889221191406, 0.19369275867938995, 0.14382655918598175, 0.11848833411931992, 0.1565011888742447, 0.2172653079032898, 0.09449362754821777, 0.10632144659757614, 0.2177293300628662, 0.14170654118061066, 0.15958379209041595, 0.1271229386329651, 0.1290907859802246, 0.13159270584583282, 0.14572033286094666, 0.22035744786262512, 0.13746528327465057, 0.09402340650558472, 0.13368573784828186, 0.11652641743421555, 0.1855889856815338, 0.1006418988108635, 0.07278663665056229, 0.2322472333908081, 0.18408294022083282, 0.15137536823749542, 0.11055551469326019, 0.18563419580459595, 0.15973182022571564, 0.12313122302293777, 0.11698367446660995, 0.1366644650697708, 0.20925605297088623, 0.15839502215385437, 0.11827402561903, 0.17572090029716492, 0.08303733915090561, 0.09318063408136368, 0.12201099842786789, 0.0749487578868866, 0.06349186599254608, 0.13393956422805786, 0.1581103801727295, 0.2271672785282135, 0.17690809071063995, 0.15714126825332642, 0.21699278056621552, 0.13893717527389526, 0.18211336433887482, 0.09982114285230637, 0.14457106590270996, 0.15449926257133484, 0.19132328033447266, 0.08729223161935806, 0.16494834423065186, 0.16863389313220978, 0.1376524120569229, 0.7130091786384583, 1.2139501571655273, 0.5750488638877869, 0.560314953327179, 0.6308456659317017, 0.9360244274139404, 1.6693099737167358, 0.8733837604522705, 0.5943053960800171, 1.237849235534668, 0.45181629061698914, 0.5896739959716797, 1.5699148178100586, 1.2047083377838135, 1.7173105478286743, 0.9787786602973938, 1.07440185546875, 1.152933955192566, 1.0861808061599731, 1.195189118385315, 0.9416031241416931, 0.9831759929656982, 1.5177849531173706, 0.9502897262573242, 1.0051392316818237, 1.2382668256759644, 0.7779080271720886, 1.6903120279312134, 1.2049200534820557, 1.645197868347168, 1.033501148223877, 0.91459059715271, 0.9889761209487915, 0.9809511303901672, 1.1098263263702393, 1.3730286359786987, 1.077109694480896, 1.7043087482452393, 0.7182624936103821, 0.8997322916984558, 0.571984052658081, 0.9892821311950684, 1.419250726699829, 0.9274500012397766, 1.1156717538833618, 0.746952474117279, 1.4697370529174805, 1.2043812274932861, 0.8245972990989685, 0.9335407614707947, 0.8946280479431152, 1.5422649383544922, 1.3750970363616943, 1.1791675090789795, 0.8815121054649353, 0.6833671927452087, 0.8441448211669922, 0.8970282673835754, 0.8093594908714294, 1.3561041355133057, 0.7231078147888184, 0.9514188766479492, 1.1098121404647827, 1.334192156791687, 0.8214109539985657, 0.5842809081077576, 0.5236383676528931, 1.022684931755066, 0.7137947082519531, 0.8333733677864075, 1.4057409763336182, 1.5815179347991943, 1.29502534866333, 1.3656883239746094, 1.411651611328125, 0.9447301030158997, 0.4197765290737152, 0.8083904981613159, 0.8270730376243591, 0.656178891658783, 1.2282750606536865, 0.9514014720916748, 0.7305804491043091, 1.619415521621704, 0.5981239676475525, 1.5108002424240112, 0.9848723411560059, 0.39521780610084534, 0.5837550163269043, 0.681763768196106, 1.5483163595199585, 1.0776095390319824, 0.53641676902771, 0.8790748119354248, 0.8500738143920898, 0.662535548210144, 1.392592430114746, 0.6860897541046143, 1.325472116470337, 1.4240528345108032, 0.8736651539802551, 0.7385395765304565, 1.0250396728515625, 1.0365859270095825, 0.8477156758308411, 1.4684635400772095, 1.0059878826141357, 1.1720091104507446, 1.0403921604156494, 0.7155110239982605, 1.1418960094451904, 0.7823584079742432, 0.952946126461029, 0.6507773995399475, 1.3146156072616577, 0.681583821773529, 1.297682762145996, 0.9532643556594849, 1.5845730304718018, 1.2235788106918335, 1.2033138275146484, 0.6299726963043213, 1.2806930541992188, 1.293280005455017, 0.8029205203056335, 1.1493072509765625, 1.2004728317260742, 1.489388108253479, 0.8012548685073853, 1.0572444200515747, 0.9308308362960815, 1.027162790298462, 1.15775465965271, 1.373516321182251, 0.8774113059043884, 0.9455605745315552, 1.2776875495910645, 1.2953922748565674, 0.7123783826828003, 0.4106324315071106, 1.5551315546035767, 0.7948530316352844, 0.6639618277549744, 1.4219964742660522, 1.6117746829986572, 0.7860355377197266, 0.5888955593109131, 0.6946857571601868, 0.7886900305747986, 0.5964944958686829, 0.979640781879425, 0.9568710327148438, 1.1662139892578125, 1.7648394107818604, 1.2426079511642456, 1.094435214996338, 1.0851986408233643, 0.47934526205062866, 0.7478922009468079, 0.8842515349388123, 1.247645616531372, 0.8837785720825195, 1.120530605316162, 0.6741517782211304, 1.2693297863006592, 0.4920044541358948, 0.6561664342880249, 1.3459103107452393, 0.9958238005638123, 1.3304704427719116, 1.4309208393096924, 0.8460603952407837, 1.7014144659042358, 1.2257304191589355, 0.9960389733314514, 0.6790943145751953, 0.8616707921028137, 1.3425899744033813, 0.8443179130554199, 1.2935922145843506, 0.7035015225410461, 0.7380631566047668, 1.5409122705459595, 0.723294734954834, 0.8969157338142395, 1.6584124565124512, 1.484513521194458, 0.6809136271476746, 0.8244315981864929, 1.3175311088562012, 2.1020073890686035, 1.2443572282791138, 1.439931869506836, 0.9159957766532898, 0.6836087107658386, 0.8337265849113464, 1.495919108390808, 0.7023531198501587, 1.0013749599456787, 0.9602069854736328, 0.8136163949966431, 1.115041971206665, 0.5723313689231873, 1.0742838382720947, 1.2851492166519165, 0.7193238139152527, 1.0923155546188354, 1.1059786081314087, 0.8151472210884094, 0.7164252400398254, 0.6982597708702087, 1.4735033512115479, 1.755268931388855, 1.3548634052276611, 0.7453794479370117, 1.2005034685134888, 0.8547412157058716, 0.9460785984992981, 1.1131170988082886, 0.41241762042045593, 1.200207233428955, 0.8438963890075684, 1.5954554080963135, 0.6517723798751831, 0.6404861211776733, 0.48809608817100525, 1.466299057006836, 1.0842845439910889, 0.7297685742378235, 1.1081198453903198, 0.797624945640564, 0.5875988006591797, 0.8434707522392273, 1.0161741971969604, 1.3859596252441406, 0.7911558151245117, 1.104001760482788, 0.8561245799064636, 1.0498381853103638, 1.2775861024856567, 1.8505034446716309, 0.8428897857666016, 0.8663128614425659, 0.7081402540206909, 0.9046503901481628, 1.172000765800476, 1.1009626388549805, 0.7213513255119324, 1.209360957145691, 1.6796228885650635, 1.30281400680542, 1.4310619831085205, 1.1417690515518188, 0.5541627407073975, 0.5958319902420044, 0.7808405160903931, 0.8548628091812134, 0.8647522330284119, 1.1715465784072876, 1.506091594696045, 0.5357214212417603, 1.2818435430526733, 1.0974045991897583, 1.893676996231079, 0.9151186943054199, 0.6822856068611145, 1.2933868169784546, 1.0873194932937622, 0.7081173062324524, 0.9508000612258911, 0.9176632761955261, 0.6431347727775574, 0.693570077419281, 0.6582832336425781, 0.9552656412124634, 0.9010814428329468, 0.9952723979949951, 1.355245590209961, 1.0850895643234253, 1.1949148178100586, 1.3928132057189941, 0.7250964045524597, 1.1501781940460205, 0.5830408930778503, 1.3908636569976807, 0.7059993743896484, 1.2435184717178345, 0.9786680340766907, 1.2709137201309204, 0.9484879970550537, 1.0713648796081543, 1.404134750366211, 0.9850010275840759, 1.46074640750885, 1.211536169052124, 1.0950602293014526, 0.7219082713127136, 1.3309136629104614, 1.0712285041809082, 1.0959750413894653, 23.9974365234375, 93.42920684814453, 32.23331832885742, 93.21517181396484, 53.711971282958984, 74.56431579589844, 195.4875030517578, 50.6112060546875, 32.57380676269531, 68.59760284423828, 111.60663604736328, 137.91287231445312, 88.10747528076172, 19.968536376953125, 58.943450927734375, 84.61870574951172, 94.7620620727539, 22.36224365234375, 76.5114517211914, 110.2728271484375, 23.401824951171875, 63.60834503173828, 22.609619140625, 73.95864868164062, 112.28336334228516, 36.53264236450195, 67.3065185546875, 77.775146484375, 69.19224548339844, 163.78260803222656, 94.07686614990234, 56.44180679321289, 58.21387481689453, 63.41326904296875, 80.88838958740234, 143.48953247070312, 78.03024291992188, 41.342987060546875, 103.36595153808594, 28.558568954467773, 55.4158935546875, 29.490375518798828, 116.44058227539062, 106.98491668701172, 158.81057739257812, 77.65042114257812, 35.036590576171875, 102.87984466552734, 65.98800659179688, 65.0196533203125, 167.542724609375, 85.39156341552734, 72.69269561767578, 88.93892669677734, 102.23989868164062, 53.47529983520508, 75.43572998046875, 52.795223236083984, 118.68255615234375, 32.460453033447266, 31.162338256835938, 88.06157684326172, 80.88727569580078, 42.94912338256836, 74.1581039428711, 102.33780670166016, 33.43365478515625, 134.70361328125, 92.81285095214844, 156.192138671875, 113.20757293701172, 77.0361328125, 32.02164840698242, 135.711181640625, 46.8876953125, 106.44805145263672, 113.38714599609375, 55.99892807006836, 29.082792282104492, 197.146240234375, 22.77398681640625, 74.984619140625, 79.9062271118164, 67.58206176757812, 78.03628540039062, 34.03266906738281, 26.379892349243164, 21.57563591003418, 72.5484619140625, 23.0953369140625, 33.31216049194336, 23.158842086791992, 96.5741195678711, 55.32813262939453, 181.6515655517578, 104.9388427734375, 112.572265625, 29.641359329223633, 37.3116455078125, 283.6527099609375, 139.98426818847656, 55.62373733520508, 49.515174865722656, 61.74467468261719, 98.12835693359375, 36.5628662109375, 68.82740020751953, 72.48147583007812, 39.70878601074219, 80.22390747070312, 90.09233856201172, 109.11064910888672, 33.230220794677734, 30.866483688354492, 102.32196044921875, 59.0994873046875, 22.386600494384766, 143.35076904296875, 120.71492004394531, 54.5439453125, 148.85296630859375, 74.951416015625, 136.90765380859375, 55.713436126708984, 47.31374740600586, 71.80005645751953, 36.866790771484375, 116.59059143066406, 61.158504486083984, 65.18791961669922, 18.71656608581543, 26.214017868041992, 27.33807373046875, 28.062528610229492, 30.763534545898438, 115.52892303466797, 74.38714599609375, 71.91680145263672, 85.2459716796875, 17.584991455078125, 32.2471923828125, 34.64866256713867, 74.63623046875, 28.3714599609375, 46.702205657958984, 28.887542724609375, 86.0859375, 51.43070983886719, 18.33380126953125, 93.25244140625, 125.72555541992188, 99.05706787109375, 21.990291595458984, 101.2586669921875, 55.42711639404297, 209.02403259277344, 35.3507080078125, 69.11740112304688, 78.62332916259766, 41.69431686401367, 102.8773422241211, 138.16000366210938, 79.97805786132812, 81.35481262207031, 36.649715423583984, 110.03218841552734, 63.87744903564453, 52.66423797607422, 108.41177368164062, 91.20052337646484, 114.93204498291016, 32.30658721923828, 164.29443359375, 182.9213104248047, 117.652587890625, 33.717010498046875, 38.46443176269531, 31.8426513671875, 118.183349609375, 50.1588134765625, 121.60894012451172, 70.64522552490234, 165.99351501464844, 92.9896011352539, 40.10296630859375, 16.037261962890625, 189.786865234375, 82.18572998046875, 40.36042022705078, 56.68548583984375, 214.0596466064453, 29.823699951171875, 28.626373291015625, 51.141292572021484, 224.07774353027344, 204.78233337402344, 57.108524322509766, 29.914125442504883, 14.0460205078125, 31.71295166015625, 121.97372436523438, 120.19482421875, 55.67864990234375, 40.11367416381836, 37.89626693725586, 54.616790771484375, 66.14702606201172, 126.0467529296875, 70.07369995117188, 122.3138656616211, 55.649715423583984, 69.50094604492188, 64.2459716796875, 70.41326904296875, 44.01433563232422, 52.290130615234375, 163.72857666015625, 99.02567291259766, 75.59906768798828, 103.7116470336914, 131.20091247558594, 55.65155029296875, 18.99309539794922, 65.44378662109375, 57.926116943359375, 65.01239013671875, 132.88107299804688, 128.24037170410156, 101.3595962524414, 86.24993896484375, 27.6116943359375, 64.729736328125, 39.29307174682617, 192.17431640625, 48.90643310546875, 183.39990234375, 47.0156135559082, 200.3924560546875, 29.9600830078125, 66.69580078125, 29.505887985229492, 28.218204498291016, 65.85523986816406, 47.98276901245117, 83.85346221923828, 94.16899871826172, 30.529491424560547, 102.25450897216797, 64.91682434082031, 107.7635726928711, 24.13325309753418, 57.1746826171875, 44.0103759765625, 73.74920654296875, 29.72053337097168, 126.21245574951172, 55.204647064208984, 43.9912109375, 23.625492095947266, 78.81095123291016, 117.30179595947266, 21.04473876953125, 49.55420684814453, 172.5966796875, 35.929115295410156, 17.10906982421875, 67.35381317138672, 100.56352996826172, 64.33110046386719, 161.9013671875, 30.834197998046875, 58.543270111083984, 49.37396240234375, 177.666748046875, 34.38528060913086, 40.986629486083984, 80.45223999023438, 66.78076171875, 47.35658645629883, 175.89291381835938, 26.416744232177734, 37.668121337890625, 19.578521728515625, 121.54771423339844, 212.92041015625, 131.27023315429688, 14.230789184570312, 126.7244873046875, 88.30119323730469, 96.04513549804688, 178.26670837402344, 77.85077667236328, 107.361572265625, 20.97821044921875, 30.38785171508789, 121.0432357788086, 204.553466796875, 92.61113739013672, 24.763397216796875, 110.29396057128906, 3.3884875774383545, 2.0127382278442383, 2.0447683334350586, 3.3734042644500732, 3.1056454181671143, 1.5986601114273071, 2.5829339027404785, 1.8442106246948242, 2.3607983589172363, 2.3729946613311768, 2.955277681350708, 2.360640525817871, 1.7366994619369507, 2.9314682483673096, 1.1527442932128906, 2.706683397293091, 2.9857988357543945, 1.8963903188705444, 1.222212791442871, 1.6987011432647705, 1.9714428186416626, 1.4026641845703125, 1.7562322616577148, 2.3205156326293945, 2.5888607501983643, 1.7886407375335693, 2.991020679473877, 1.6943482160568237, 2.1653897762298584, 2.4615085124969482, 2.70296573638916, 3.0802950859069824, 2.4483585357666016, 2.1321327686309814, 1.890705943107605, 3.6627821922302246, 1.4341607093811035, 2.4086923599243164, 2.8481547832489014, 2.5950822830200195, 2.2771832942962646, 2.2097206115722656, 2.3851003646850586, 2.81744122505188, 2.531439781188965, 2.2245378494262695, 2.6923859119415283, 2.5968081951141357, 1.4849131107330322, 1.4288244247436523, 3.0409348011016846, 2.8034563064575195, 2.732802152633667, 2.1665713787078857, 2.6291465759277344, 2.202594041824341, 1.5993584394454956, 2.4193854331970215, 1.786520004272461, 1.8061861991882324, 2.184224843978882, 1.650160789489746, 2.4406230449676514, 2.1594114303588867, 1.9233874082565308, 1.475329875946045, 1.9247815608978271, 1.4405525922775269, 1.1828413009643555, 1.7405880689620972, 2.9640889167785645, 2.9544055461883545, 2.420424461364746, 2.688613176345825, 1.9282680749893188, 2.3084897994995117, 1.887011170387268, 2.3868069648742676, 2.7446281909942627, 1.43009352684021, 1.3898217678070068, 3.0857574939727783, 1.656264305114746, 2.778461456298828, 2.2989933490753174, 3.684128999710083, 2.5887179374694824, 3.6072299480438232, 1.4997930526733398, 1.9597169160842896, 1.4809551239013672, 1.3554564714431763, 2.1539506912231445, 1.6690385341644287, 1.5779485702514648, 2.5171115398406982, 2.7287707328796387, 1.884932518005371, 2.284918785095215, 2.118457555770874, 3.1168432235717773, 2.450911283493042, 2.5544381141662598, 1.7258634567260742, 2.6712028980255127, 1.6199897527694702, 1.4372837543487549, 1.4039210081100464, 2.2449426651000977, 2.694983959197998, 2.1686437129974365, 2.2354624271392822, 2.2834770679473877, 2.4417672157287598, 2.8130388259887695, 2.0415167808532715, 1.7720417976379395, 1.3316010236740112, 2.0143651962280273, 2.8696696758270264, 1.9476079940795898, 1.8730840682983398, 2.999394178390503, 2.2164933681488037, 2.1727421283721924, 2.613013744354248, 3.1587727069854736, 2.6460673809051514, 3.422926664352417, 2.2999868392944336, 3.249955415725708, 1.9117478132247925, 1.7103487253189087, 1.8668715953826904, 2.134263038635254, 3.500105857849121, 2.884500026702881, 2.8033668994903564, 2.837419271469116, 2.856201410293579, 2.1310532093048096, 1.6584185361862183, 1.5423883199691772, 2.951159715652466, 1.8598030805587769, 1.5979920625686646, 2.4890170097351074, 1.4620990753173828, 1.2262036800384521, 1.7279385328292847, 3.0150508880615234, 3.5391807556152344, 2.1041784286499023, 1.9421868324279785, 3.4391984939575195, 2.655611753463745, 1.8271557092666626, 1.1250481605529785, 2.1886823177337646, 2.5789263248443604, 2.0518240928649902, 1.71811842918396, 2.5942394733428955, 3.6554996967315674, 1.1637334823608398, 1.4552602767944336, 2.7457797527313232, 1.8851302862167358, 1.5433273315429688, 1.285166621208191, 2.4119386672973633, 2.639826536178589, 1.374098777770996, 1.7596960067749023, 1.5446633100509644, 2.308150291442871, 1.8762041330337524, 2.259016513824463, 2.576176404953003, 1.6369696855545044, 2.0969724655151367, 2.5289525985717773, 3.051175355911255, 2.540374755859375, 3.14772891998291, 2.1025514602661133, 3.5851683616638184, 1.687389850616455, 3.2541427612304688, 1.421614646911621, 1.3907989263534546, 2.413111686706543, 1.1760129928588867, 3.023754119873047, 3.1587774753570557, 2.3927011489868164, 1.8283246755599976, 1.861166000366211, 2.4716708660125732, 3.5728728771209717, 1.3981237411499023, 2.257946252822876, 2.9322328567504883, 1.312031626701355, 3.111497640609741, 2.7540385723114014, 2.788702964782715, 3.0864152908325195, 3.0589191913604736, 1.637080192565918, 2.9540483951568604, 2.0591955184936523, 2.7363555431365967, 1.7997312545776367, 3.668757438659668, 3.291693687438965, 1.5230038166046143, 1.9958410263061523, 2.329728126525879, 2.923114061355591, 2.3221020698547363, 1.8018462657928467, 2.620004177093506, 2.0420777797698975, 1.3969521522521973, 2.111703872680664, 2.647449254989624, 2.3279809951782227, 2.099130868911743, 2.2495930194854736, 1.5426644086837769, 1.8800970315933228, 2.3458921909332275, 3.328982353210449, 2.165156602859497, 3.385455846786499, 2.865856170654297, 1.8989077806472778, 1.887808918952942, 1.570300817489624, 2.6868748664855957, 2.970104932785034, 1.7433849573135376, 3.431820869445801, 2.704801082611084, 2.8797216415405273, 2.0541162490844727, 3.5801384449005127, 2.3276662826538086, 2.600562334060669, 3.1858489513397217, 2.260685920715332, 2.350245237350464, 1.3311100006103516, 2.263075828552246, 2.0809266567230225, 1.6200637817382812, 2.057016611099243, 1.4546051025390625, 2.061258554458618, 2.625659227371216, 3.6566076278686523, 1.789042592048645, 2.3921077251434326, 1.3324010372161865, 2.6879990100860596, 1.670680046081543, 1.3285094499588013, 2.22184681892395, 2.6876628398895264, 2.4667904376983643, 3.9185729026794434, 2.832202196121216, 2.4845774173736572, 2.933964729309082, 2.021836996078491, 1.5269020795822144, 2.9980571269989014, 2.5339267253875732, 2.483332872390747, 2.0551226139068604, 2.6843011379241943, 2.5444862842559814, 2.542339563369751, 2.019892930984497, 3.720485210418701, 1.7821378707885742, 2.8181121349334717, 1.7349920272827148, 2.332268714904785, 2.1554322242736816, 1.793213963508606, 2.152564764022827, 2.4291017055511475, 2.880460739135742, 1.599131464958191, 2.0392637252807617, 1.7930223941802979, 1.9894874095916748, 1.7490780353546143, 0.1535596251487732, 0.18346011638641357, 0.1692311018705368, 0.2449750155210495, 0.11838577687740326, 0.2086300402879715, 0.12516561150550842, 0.16779166460037231, 0.16629277169704437, 0.11879386752843857, 0.08442065119743347, 0.13811586797237396, 0.1557881385087967, 0.17529639601707458, 0.12451750785112381, 0.12287170439958572, 0.15906226634979248, 0.09560925513505936, 0.15148775279521942, 0.13203588128089905, 0.17536933720111847, 0.171322301030159, 0.16523078083992004, 0.15451277792453766, 0.11045753210783005, 0.13632194697856903, 0.15841183066368103, 0.27502894401550293, 0.1741172969341278, 0.135106161236763, 0.13036175072193146, 0.21373224258422852, 0.21297219395637512, 0.11838478595018387, 0.11097988486289978, 0.23394931852817535, 0.15638600289821625, 0.13006708025932312, 0.11101564019918442, 0.1727525293827057, 0.14713437855243683, 0.15769954025745392, 0.20476098358631134, 0.1422533392906189, 0.18542909622192383, 0.14660266041755676, 0.1736827790737152, 0.17981933057308197, 0.18520835041999817, 0.1383601576089859, 0.10319744050502777, 0.13348443806171417, 0.14030446112155914, 0.1754668802022934, 0.20082968473434448, 0.14167346060276031, 0.1646007001399994, 0.18211892247200012, 0.20379981398582458, 0.1600516438484192, 0.08496809005737305, 0.0739283487200737, 0.1424688845872879, 0.223420649766922, 0.15890178084373474, 0.10884164273738861, 0.14173030853271484, 0.143079474568367, 0.12971724569797516, 0.17011038959026337, 0.08874386548995972, 0.15877801179885864, 0.11002060770988464, 0.17661915719509125, 0.16382281482219696, 0.13913863897323608, 0.152561217546463, 0.13570605218410492, 0.11597055941820145, 0.13819707930088043, 0.13575343787670135, 0.1829911321401596, 0.16020019352436066, 0.1032361313700676, 0.12190727144479752, 0.11533979326486588, 0.1772913634777069, 0.15615057945251465, 0.15632951259613037, 0.07394923269748688, 0.12921595573425293, 0.12079315632581711, 0.1442582905292511, 0.1932092010974884, 0.13580669462680817, 0.12066030502319336, 0.11387891322374344, 0.13911637663841248, 0.15860706567764282, 0.09589308500289917, 0.1602129489183426, 0.09707513451576233, 0.12932759523391724, 0.10780036449432373, 0.18450777232646942, 0.14148159325122833, 0.14511750638484955, 0.08680879324674606, 0.1371520608663559, 0.16829361021518707, 0.11431340873241425, 0.20265398919582367, 0.22518110275268555, 0.12606503069400787, 0.16236229240894318, 0.21649226546287537, 0.136784166097641, 0.20476798713207245, 0.19275210797786713, 0.08916004002094269, 0.11371640861034393, 0.17950116097927094, 0.14793366193771362, 0.08801290392875671, 0.11943402886390686, 0.14201056957244873, 0.18741703033447266, 0.1720224767923355, 0.12326844036579132, 0.13096892833709717, 0.1533949077129364, 0.09594251215457916, 0.16008803248405457, 0.142680361866951, 0.14865174889564514, 0.19109678268432617, 0.18640540540218353, 0.16493980586528778, 0.09992413967847824, 0.10375981777906418, 0.14867322146892548, 0.15097440779209137, 0.20841288566589355, 0.1473570168018341, 0.05611552298069, 0.2135167419910431, 0.13297614455223083, 0.09181781858205795, 0.2134006768465042, 0.06545024365186691, 0.1557164192199707, 0.16925014555454254, 0.20180873572826385, 0.13552695512771606, 0.20188403129577637, 0.12095221877098083, 0.19173966348171234, 0.13179853558540344, 0.19731147587299347, 0.12452719360589981, 0.2184297889471054, 0.1591351181268692, 0.14037597179412842, 0.2172621488571167, 0.1239393800497055, 0.17479845881462097, 0.10921932011842728, 0.16820676624774933, 0.17371466755867004, 0.12045016884803772, 0.14481329917907715, 0.13298900425434113, 0.1303185075521469, 0.08005983382463455, 0.14814458787441254, 0.11764945834875107, 0.1203087568283081, 0.13751521706581116, 0.06131598353385925, 0.11602088063955307, 0.12380880117416382, 0.13960176706314087, 0.10648085176944733, 0.17126120626926422, 0.10156206041574478, 0.19650563597679138, 0.19140838086605072, 0.14280439913272858, 0.2255694717168808, 0.18190135061740875, 0.21009822189807892, 0.17487652599811554, 0.06844732910394669, 0.16997814178466797, 0.19704261422157288, 0.1822158843278885, 0.13483335077762604, 0.16813945770263672, 0.13518750667572021, 0.10102125257253647, 0.14599637687206268, 0.1823187917470932, 0.10993491858243942, 0.14986057579517365, 0.1437234878540039, 0.13377155363559723, 0.12461642920970917, 0.10618360340595245, 0.13023117184638977, 0.12727101147174835, 0.1586979627609253, 0.11189436912536621, 0.15298530459403992, 0.11682850867509842, 0.12458871304988861, 0.1443338692188263, 0.10358548164367676, 0.11936470866203308, 0.17004819214344025, 0.09050413221120834, 0.1399707794189453, 0.14212147891521454, 0.20823794603347778, 0.1716712862253189, 0.17114928364753723, 0.12563879787921906, 0.1589139699935913, 0.16784308850765228, 0.11883563548326492, 0.10986537486314774, 0.15577083826065063, 0.18547473847866058, 0.0986599549651146, 0.1255636215209961, 0.09843724966049194, 0.17668159306049347, 0.16378533840179443, 0.15635013580322266, 0.1757393181324005, 0.19480666518211365, 0.10817072540521622, 0.14189743995666504, 0.17281422019004822, 0.15091174840927124, 0.14030355215072632, 0.148713618516922, 0.18647101521492004, 0.1720547378063202, 0.18225547671318054, 0.11299870163202286, 0.08627298474311829, 0.16378259658813477, 0.12652955949306488, 0.17260155081748962, 0.18421998620033264, 0.18630944192409515, 0.11230222135782242, 0.08320280909538269, 0.186275914311409, 0.08119085431098938, 0.15402765572071075, 0.19556006789207458, 0.14315646886825562, 0.11731158941984177, 0.16226066648960114, 0.08601878583431244, 0.1558617800474167, 0.1404781937599182, 0.16167350113391876, 0.12036681920289993, 0.12351641058921814, 0.1354936957359314, 0.12899981439113617, 0.14406085014343262, 0.1407153159379959, 0.14065364003181458, 0.16738061606884003, 0.1830156296491623, 0.13585209846496582, 0.134994775056839, 0.17123866081237793, 0.11087378859519958, 0.12051534652709961, 0.17645195126533508, 0.09172619879245758, 0.1823817789554596, 0.1495748609304428, 0.16799816489219666, 0.13433459401130676, 0.11641965806484222, 0.10017869621515274, 0.1422078013420105, 0.1611030548810959, 0.07836658507585526, 0.15287338197231293, 0.22817271947860718, 0.14215028285980225, 0.18321771919727325, 0.19885410368442535, 0.17015452682971954, 1.8180001974105835, 1.1553301811218262, 1.1610243320465088, 1.9648545980453491, 0.618757963180542, 1.1163173913955688, 1.445338249206543, 0.8421182036399841, 1.292441964149475, 1.2112581729888916, 1.1752713918685913, 0.6115133762359619, 1.3291863203048706, 0.6784583926200867, 1.002629041671753, 1.1929763555526733, 1.391404390335083, 0.9839911460876465, 1.0686758756637573, 1.0309340953826904, 1.500535249710083, 0.5674805045127869, 1.1785438060760498, 0.9169735312461853, 1.0476057529449463, 1.552911400794983, 1.0947871208190918, 1.3242337703704834, 0.8436600565910339, 1.0273525714874268, 1.0750442743301392, 1.1411242485046387, 1.1696276664733887, 1.1247375011444092, 1.2019401788711548, 0.9475134015083313, 1.337527871131897, 1.1049396991729736, 1.3878991603851318, 1.0106887817382812, 1.696106195449829, 1.296431541442871, 1.3881587982177734, 1.2034778594970703, 1.2125300168991089, 0.7018752694129944, 0.9326016306877136, 0.8477145433425903, 1.1143145561218262, 1.0121521949768066, 1.1021552085876465, 1.4481741189956665, 1.2758779525756836, 0.8744379281997681, 1.7370027303695679, 1.092477560043335, 1.0424610376358032, 1.8868318796157837, 0.807140052318573, 0.9089909791946411, 0.9021642804145813, 0.7469058036804199, 1.1546728610992432, 1.2851284742355347, 1.5095787048339844, 1.5877115726470947, 1.5249996185302734, 0.8386933207511902, 2.1088991165161133, 1.1886076927185059, 1.7980360984802246, 0.705215573310852, 0.8260923624038696, 1.515860915184021, 1.0344161987304688, 1.546939492225647, 1.216322422027588, 1.8752615451812744, 1.2873995304107666, 1.033277988433838, 1.3932794332504272, 1.2959415912628174, 1.006561517715454, 0.6926758289337158, 1.7181360721588135, 0.6167223453521729, 1.2412464618682861, 1.7440217733383179, 1.0164555311203003, 0.9209480285644531, 1.3088821172714233, 1.0378931760787964, 1.18326997756958, 1.1315757036209106, 0.7691702246665955, 0.9782444834709167, 0.8272852897644043, 2.1385278701782227, 1.689003586769104, 1.2977646589279175, 0.5041087865829468, 1.1510851383209229, 0.5123056769371033, 1.2427198886871338, 0.9922825694084167, 0.59073406457901, 1.7613821029663086, 1.2749578952789307, 1.0795998573303223, 1.743566870689392, 0.8512493968009949, 0.9952237010002136, 1.1010226011276245, 0.8906533718109131, 1.6120848655700684, 1.27487313747406, 1.0759721994400024, 1.7431875467300415, 0.6065131425857544, 0.9714269042015076, 1.666717529296875, 1.3218047618865967, 1.4486802816390991, 1.2841503620147705, 1.3803554773330688, 1.1586774587631226, 1.0574249029159546, 0.6144105195999146, 1.0026440620422363, 1.3873058557510376, 0.512245237827301, 0.8082587718963623, 1.116707444190979, 1.1914091110229492, 1.4119888544082642, 0.9850109815597534, 0.7534863352775574, 0.7602154612541199, 0.9033209085464478, 0.6476936340332031, 1.0676382780075073, 1.6986770629882812, 1.0199222564697266, 1.3184646368026733, 0.723724365234375, 1.3735237121582031, 1.6220468282699585, 1.6948693990707397, 1.328493356704712, 1.2923572063446045, 1.2721933126449585, 1.1247739791870117, 1.2967584133148193, 1.5031992197036743, 0.9267698526382446, 1.065931797027588, 1.323419213294983, 1.1629784107208252, 1.5248501300811768, 0.7290072441101074, 1.1579763889312744, 1.2249646186828613, 1.6122738122940063, 0.8153649568557739, 1.2324379682540894, 1.2388584613800049, 1.0823312997817993, 1.1068305969238281, 1.331262469291687, 1.174045205116272, 0.6677784323692322, 1.1443318128585815, 1.565690279006958, 1.3268153667449951, 1.6473482847213745, 0.7900002598762512, 1.7497680187225342, 1.2173603773117065, 1.3388322591781616, 1.2322783470153809, 0.9630829691886902, 0.7624090313911438, 1.2691473960876465, 0.4712326228618622, 0.9842700958251953, 1.4562395811080933, 0.5495780110359192, 1.6875807046890259, 1.2806578874588013, 0.8399966359138489, 1.1055494546890259, 1.0265883207321167, 0.9628487825393677, 1.4909467697143555, 1.0473514795303345, 1.216150164604187, 1.810280442237854, 1.633994460105896, 1.2929563522338867, 0.8349511027336121, 1.108510136604309, 1.1354446411132812, 0.5462210774421692, 0.8197070360183716, 1.011968731880188, 0.9327369332313538, 1.373834490776062, 1.0687923431396484, 0.9137988090515137, 0.8684222102165222, 1.1975266933441162, 1.1537013053894043, 0.7877505421638489, 1.460277795791626, 0.9686358571052551, 1.0209345817565918, 0.7652482390403748, 1.152406930923462, 1.2951923608779907, 0.6227350234985352, 1.6325170993804932, 1.2687050104141235, 1.084761142730713, 0.8600766658782959, 1.117688536643982, 1.1920372247695923, 0.5983481407165527, 1.6476414203643799, 0.29255515336990356, 1.2380127906799316, 1.4494211673736572, 0.8420454263687134, 0.6293016076087952, 0.7556608319282532, 0.8623130321502686, 0.8692208528518677, 0.7797195911407471, 1.4022424221038818, 1.3092620372772217, 1.2858457565307617, 1.2243082523345947, 0.648018479347229, 0.8468020558357239, 1.191158413887024, 1.1188311576843262, 0.9476017355918884, 0.637936532497406, 0.7476735711097717, 1.153944969177246, 1.3455572128295898, 1.1485576629638672, 1.3551424741744995, 1.4809900522232056, 1.413403034210205, 0.858199417591095, 0.6954109072685242, 0.7308281064033508, 0.7097461819648743, 1.3622477054595947, 0.6273890137672424, 0.6765167117118835, 0.8991110920906067, 1.2400882244110107, 1.0577882528305054, 1.3541619777679443, 0.9792092442512512, 0.3792901635169983, 1.1669692993164062, 0.8976191282272339, 1.6258465051651, 0.6735712885856628, 1.2347540855407715, 1.0394043922424316, 0.4512987434864044, 1.3291643857955933, 0.9186957478523254, 1.2775471210479736, 1.1033855676651, 0.7490372061729431, 0.6281829476356506, 1.2525088787078857, 1.0273815393447876, 1.1821231842041016, 0.8429585695266724, 0.6948679089546204, 0.7445152401924133, 2.3616867065429688, 0.7526284456253052, 1.1044261455535889, 1.522233247756958, 1.0401240587234497, 1.2524446249008179, 0.8548165559768677, 1.1261664628982544, 1.377113938331604, 1.5435466766357422, 1.8572319746017456, 0.9958796501159668, 1.229308009147644, 1.7609679698944092, 50.25215530395508, 51.72163009643555, 28.0859375, 41.96360397338867, 31.55877685546875, 119.79745483398438, 50.03921127319336, 29.31243896484375, 23.71148681640625, 28.333518981933594, 104.03812408447266, 21.18829345703125, 63.23974609375, 47.11960983276367, 155.58157348632812, 29.747501373291016, 22.174991607666016, 228.1123046875, 37.21799087524414, 38.98125457763672, 41.82928466796875, 26.03192901611328, 104.75115966796875, 105.234375, 39.56414794921875, 56.13421630859375, 23.225341796875, 140.30511474609375, 107.99259185791016, 53.970462799072266, 96.16888427734375, 149.86431884765625, 24.7144775390625, 104.61576080322266, 19.86695098876953, 88.21170043945312, 123.98158264160156, 23.311689376831055, 26.933866500854492, 37.159881591796875, 75.3062744140625, 112.197509765625, 19.31839370727539, 45.3447265625, 109.43404388427734, 78.93364715576172, 55.612674713134766, 53.932952880859375, 182.07383728027344, 30.3582820892334, 62.0997314453125, 39.90524673461914, 93.36431121826172, 56.343719482421875, 29.39985466003418, 30.3304443359375, 33.14869689941406, 95.1382827758789, 101.82904052734375, 87.54390716552734, 34.224700927734375, 27.390869140625, 39.537567138671875, 103.35400390625, 117.56002044677734, 24.57376480102539, 56.70896530151367, 56.00822067260742, 138.72515869140625, 150.51763916015625, 129.78158569335938, 142.90109252929688, 22.016742706298828, 16.159610748291016, 51.40315246582031, 24.44146728515625, 25.507280349731445, 34.609619140625, 20.07550048828125, 78.98416137695312, 189.3485107421875, 56.22754669189453, 176.2887420654297, 82.80620574951172, 85.14004516601562, 170.4317169189453, 87.08882904052734, 21.089946746826172, 71.55419921875, 82.5545654296875, 19.105018615722656, 63.57693099975586, 61.46743392944336, 114.74407958984375, 34.59418487548828, 39.44189453125, 41.970672607421875, 36.44342041015625, 92.28911590576172, 68.35818481445312, 163.269287109375, 132.52035522460938, 80.35693359375, 27.238290786743164, 24.393470764160156, 89.9173583984375, 46.91211700439453, 58.744300842285156, 28.163330078125, 38.88116455078125, 147.87808227539062, 37.3041877746582, 59.45619583129883, 27.486112594604492, 129.84872436523438, 57.09013366699219, 80.5213394165039, 61.06913757324219, 40.27081298828125, 76.3492202758789, 54.31390380859375, 17.04176139831543, 28.41480827331543, 33.70611572265625, 151.3887176513672, 21.96051025390625, 86.09808349609375, 70.67823791503906, 149.40911865234375, 61.811279296875, 21.899765014648438, 96.08099365234375, 160.94552612304688, 50.57667922973633, 30.274948120117188, 35.613739013671875, 68.64990997314453, 174.26605224609375, 113.67361450195312, 31.09757423400879, 134.4606170654297, 25.877626419067383, 81.8639144897461, 38.0433349609375, 34.92145919799805, 150.61203002929688, 109.56220245361328, 21.46575927734375, 34.6863899230957, 39.132720947265625, 24.411161422729492, 89.25634765625, 59.99392318725586, 197.0413360595703, 23.553373336791992, 100.09259796142578, 64.15703582763672, 108.745361328125, 107.3820571899414, 115.61910247802734, 110.13949584960938, 192.30419921875, 80.96367645263672, 17.671142578125, 67.09906005859375, 56.078216552734375, 24.998291015625, 57.770320892333984, 102.45222473144531, 91.7745132446289, 87.44256591796875, 91.95269012451172, 135.71176147460938, 97.92274475097656, 52.40151596069336, 112.00894165039062, 39.454925537109375, 50.87167739868164, 106.6728515625, 75.53960418701172, 178.0579833984375, 88.63311004638672, 18.94635009765625, 213.6893310546875, 88.75018310546875, 116.3637466430664, 98.16400146484375, 45.48047637939453, 109.23052215576172, 56.54852294921875, 55.86767578125, 109.81463623046875, 121.28023529052734, 24.329681396484375, 77.15568542480469, 22.499704360961914, 15.4803466796875, 23.95965576171875, 159.29592895507812, 80.27676391601562, 29.795379638671875, 124.73312377929688, 24.16229248046875, 55.535980224609375, 19.149383544921875, 47.62793731689453, 90.35208892822266, 119.0092544555664, 44.20937728881836, 89.89320373535156, 179.431396484375, 117.19857788085938, 56.82025146484375, 102.57171630859375, 154.43295288085938, 115.10991668701172, 81.54348754882812, 60.11367416381836, 69.94491577148438, 76.05852508544922, 44.911434173583984, 48.1702880859375, 58.446624755859375, 190.23692321777344, 72.65166473388672, 43.0322151184082, 116.8925552368164, 129.5630645751953, 143.5364990234375, 86.93257904052734, 39.99533462524414, 31.408109664916992, 164.5879669189453, 35.92303466796875, 63.966552734375, 58.7705078125, 31.868818283081055, 64.30205535888672, 174.47178649902344, 68.4615478515625, 101.24882507324219, 237.814208984375, 25.966581344604492, 128.21078491210938, 227.7626190185547, 64.85171508789062, 122.9349594116211, 69.26454162597656, 118.67398071289062, 65.4744873046875, 25.506805419921875, 76.12874603271484, 107.10607147216797, 19.9913330078125, 127.029052734375, 25.6640625, 138.8968505859375, 22.743770599365234, 41.18465805053711, 98.06753540039062, 100.58155822753906, 56.640663146972656, 20.00206756591797, 34.66584014892578, 111.10013580322266, 132.99252319335938, 132.95611572265625, 34.228702545166016, 81.92681121826172, 154.7288818359375, 98.8380355834961, 99.04259490966797, 134.3383331298828, 63.64980697631836, 35.22965621948242, 185.73780822753906, 78.72073364257812, 128.89959716796875, 40.30621337890625, 61.529754638671875, 17.415163040161133, 133.69732666015625, 22.66507339477539, 61.81296920776367, 62.565399169921875, 78.84027099609375, 95.03252410888672, 33.233558654785156, 42.74671936035156, 108.450439453125, 40.70578384399414, 60.92959213256836, 69.2735366821289, 36.19140625, 30.905868530273438, 148.65097045898438, 66.9107437133789, 107.33870697021484, 79.77749633789062, 77.64781188964844, 2.8742363452911377, 1.976374626159668, 2.237847328186035, 1.8911789655685425, 1.8018484115600586, 1.6433721780776978, 2.6839075088500977, 2.2748022079467773, 1.1596012115478516, 2.655816078186035, 3.0138304233551025, 1.744423747062683, 2.0559492111206055, 1.8575286865234375, 2.2748212814331055, 1.891493797302246, 3.014582395553589, 1.6498000621795654, 2.0641796588897705, 2.4178996086120605, 3.049903392791748, 2.5784401893615723, 3.2974061965942383, 2.4056615829467773, 1.0818413496017456, 1.54228675365448, 2.8921101093292236, 2.0263662338256836, 1.7949621677398682, 2.7948009967803955, 2.3201935291290283, 1.9701510667800903, 3.4168083667755127, 2.2284791469573975, 2.205087184906006, 2.031203508377075, 3.2050349712371826, 2.890162706375122, 2.0881435871124268, 2.894076108932495, 3.9170985221862793, 2.1356351375579834, 2.3216967582702637, 3.1116456985473633, 1.6507854461669922, 2.2905373573303223, 1.8779058456420898, 2.6821346282958984, 2.7410943508148193, 2.1529529094696045, 2.150442123413086, 2.722334623336792, 2.336510419845581, 3.1627397537231445, 2.224919319152832, 2.4657962322235107, 1.6385201215744019, 2.438107490539551, 3.1677403450012207, 1.585169792175293, 2.2518908977508545, 1.284310221672058, 1.7455406188964844, 1.6212798357009888, 2.087759017944336, 3.409865140914917, 2.2910046577453613, 2.9639062881469727, 1.823086142539978, 2.2194597721099854, 1.8926910161972046, 3.7386486530303955, 3.5132391452789307, 1.8815890550613403, 2.491251230239868, 1.994551658630371, 2.3756587505340576, 1.9495400190353394, 2.3655004501342773, 1.591347575187683, 2.107044219970703, 2.011561632156372, 1.124506950378418, 1.5871628522872925, 2.102879047393799, 1.9878554344177246, 1.9799965620040894, 1.5946511030197144, 1.8596047163009644, 2.090664863586426, 1.1891002655029297, 2.120497703552246, 2.1773483753204346, 2.6574347019195557, 1.1539362668991089, 1.6037720441818237, 2.1702756881713867, 2.8970437049865723, 2.3742189407348633, 2.151411771774292, 3.1095876693725586, 2.597632884979248, 2.891880989074707, 2.3441388607025146, 1.8966258764266968, 1.6617351770401, 3.127288341522217, 2.2697629928588867, 2.965147018432617, 1.7114461660385132, 1.7599766254425049, 2.1947786808013916, 3.0262269973754883, 2.2516896724700928, 2.3080267906188965, 2.6947503089904785, 1.3608694076538086, 3.0735156536102295, 2.182600736618042, 3.2462756633758545, 2.0444135665893555, 1.548299789428711, 1.5782021284103394, 2.3366270065307617, 2.276259422302246, 2.438370704650879, 1.7172727584838867, 2.076457977294922, 2.2925329208374023, 1.4607235193252563, 3.2711400985717773, 2.7500128746032715, 2.40887713432312, 2.8059685230255127, 1.789099097251892, 2.7968108654022217, 2.6659936904907227, 3.4643023014068604, 1.51274573802948, 2.0553627014160156, 1.4811246395111084, 1.616999626159668, 2.811246633529663, 2.730272054672241, 2.5972869396209717, 3.0266973972320557, 2.1931722164154053, 1.8260210752487183, 3.3659896850585938, 1.7012585401535034, 2.7542810440063477, 2.2469112873077393, 2.1016767024993896, 1.7365646362304688, 2.7352001667022705, 2.2288827896118164, 3.1494157314300537, 2.1487550735473633, 2.700145721435547, 2.5169553756713867, 2.7017767429351807, 3.1023900508880615, 2.1101388931274414, 1.8822476863861084, 2.5578789710998535, 1.6736727952957153, 1.8000422716140747, 3.2638332843780518, 1.6846972703933716, 2.717545747756958, 2.206653118133545, 2.3657379150390625, 1.9041873216629028, 3.013808250427246, 2.0416629314422607, 1.653483271598816, 2.1412878036499023, 2.5860495567321777, 2.3041863441467285, 3.5343034267425537, 2.0719785690307617, 2.6945624351501465, 2.4007043838500977, 2.1447458267211914, 1.4749555587768555, 2.452836036682129, 3.150864601135254, 1.6281843185424805, 1.6931819915771484, 3.0752551555633545, 2.027493476867676, 2.7053234577178955, 1.3829315900802612, 2.459467649459839, 1.7916146516799927, 2.024937629699707, 2.583754301071167, 2.44631290435791, 2.9465172290802, 3.4774999618530273, 3.116602659225464, 2.226062774658203, 3.1362199783325195, 2.8207085132598877, 2.410027027130127, 1.9193181991577148, 1.1458290815353394, 2.5323705673217773, 2.062319755554199, 2.223783254623413, 2.134030818939209, 2.309828996658325, 1.8216546773910522, 1.660677433013916, 2.6454265117645264, 2.5720906257629395, 2.0551352500915527, 3.682539939880371, 3.494169235229492, 2.4655182361602783, 2.8119826316833496, 1.8891592025756836, 2.6884970664978027, 2.4065840244293213, 3.015408754348755, 2.175816059112549, 2.442742347717285, 3.8281795978546143, 2.483718156814575, 2.128786087036133, 2.087409019470215, 2.6738390922546387, 1.806879997253418, 2.6249706745147705, 2.504045248031616, 1.2034348249435425, 1.9565105438232422, 2.401676654815674, 2.300717353820801, 1.406543493270874, 2.0241730213165283, 2.3808000087738037, 1.8722869157791138, 1.6565656661987305, 1.6301051378250122, 1.986781120300293, 2.387955904006958, 2.745110511779785, 2.3268637657165527, 2.6878867149353027, 2.6289453506469727, 2.185685873031616, 2.587855100631714, 1.629049301147461, 1.8350876569747925, 3.169463634490967, 3.1744329929351807, 2.722754955291748, 1.8412188291549683, 2.2217330932617188, 2.9322941303253174, 1.9263508319854736, 1.702528953552246, 2.090806007385254, 2.401698112487793, 1.4120022058486938, 2.4176292419433594, 1.7392492294311523, 2.0073344707489014, 1.4390449523925781, 3.2374675273895264, 2.6829943656921387, 2.096734046936035, 2.703381299972534, 1.9850798845291138, 1.7068824768066406, 2.3808908462524414, 2.4534976482391357, 1.5234802961349487, 2.241725444793701, 2.4506678581237793, 1.9613925218582153, 2.711538314819336, 2.23044490814209, 1.9462852478027344, 2.1722021102905273, 2.4293856620788574, 2.291405439376831, 3.337728261947632, 1.74704909324646, 2.0542497634887695, 2.5056827068328857, 2.3931663036346436, 1.9399791955947876, 2.408013343811035, 1.8274140357971191, 1.3081713914871216, 3.547003984451294, 3.250558376312256, 2.735518217086792, 0.11240630596876144, 0.09944061189889908, 0.19894900918006897, 0.14384222030639648, 0.20642369985580444, 0.1112281009554863, 0.08308520168066025, 0.13329140841960907, 0.18636977672576904, 0.13446617126464844, 0.16567492485046387, 0.12253005802631378, 0.10191673040390015, 0.1617649495601654, 0.16624553501605988, 0.11133970320224762, 0.17168653011322021, 0.1847776621580124, 0.1475512534379959, 0.21468497812747955, 0.10820809751749039, 0.1531478762626648, 0.14791658520698547, 0.16111597418785095, 0.1261541247367859, 0.09120237082242966, 0.10542281717061996, 0.10974878072738647, 0.1656654328107834, 0.23035447299480438, 0.1611148864030838, 0.18563206493854523, 0.13705982267856598, 0.12999777495861053, 0.13564695417881012, 0.12177631258964539, 0.1472603976726532, 0.20663507282733917, 0.1427825540304184, 0.10322003066539764, 0.08790049701929092, 0.13578177988529205, 0.14299273490905762, 0.11347642540931702, 0.11448414623737335, 0.1392359435558319, 0.11469241231679916, 0.15088731050491333, 0.15234452486038208, 0.2061890810728073, 0.06638691574335098, 0.12275312095880508, 0.14760911464691162, 0.25882476568222046, 0.09495826810598373, 0.10429893434047699, 0.14086806774139404, 0.1473497748374939, 0.12027253210544586, 0.1223112940788269, 0.14369115233421326, 0.20135588943958282, 0.11381978541612625, 0.13770468533039093, 0.10572368651628494, 0.14975863695144653, 0.17387448251247406, 0.1610592007637024, 0.10966403782367706, 0.18531496822834015, 0.16263702511787415, 0.1347752958536148, 0.13634707033634186, 0.13821972906589508, 0.16894462704658508, 0.18868033587932587, 0.12093230336904526, 0.14125458896160126, 0.10705720633268356, 0.09112580865621567, 0.1435590386390686, 0.1471201479434967, 0.08660732954740524, 0.21004170179367065, 0.1571224331855774, 0.11929738521575928, 0.14694744348526, 0.12316625565290451, 0.15568934381008148, 0.14963632822036743, 0.08192632347345352, 0.09407160431146622, 0.13422197103500366, 0.10971387475728989, 0.16605861485004425, 0.14645473659038544, 0.18759703636169434, 0.10717304050922394, 0.1348028928041458, 0.12149453908205032, 0.14563536643981934, 0.13404835760593414, 0.13127084076404572, 0.14333264529705048, 0.08904492855072021, 0.10316196084022522, 0.13334514200687408, 0.12422388046979904, 0.14198464155197144, 0.154859259724617, 0.1345590204000473, 0.20044249296188354, 0.14660578966140747, 0.2505546808242798, 0.19669586420059204, 0.17207130789756775, 0.11731148511171341, 0.22088582813739777, 0.1006830483675003, 0.21424369513988495, 0.17953841388225555, 0.13344351947307587, 0.1453286111354828, 0.14528103172779083, 0.21327029168605804, 0.1739867478609085, 0.15151651203632355, 0.07709585875272751, 0.16521915793418884, 0.15332311391830444, 0.10964550077915192, 0.13157767057418823, 0.21117602288722992, 0.1917390376329422, 0.18538039922714233, 0.1303679496049881, 0.1426914632320404, 0.18698279559612274, 0.14204619824886322, 0.15318533778190613, 0.17367465794086456, 0.14230945706367493, 0.11320704221725464, 0.13047878444194794, 0.15688984096050262, 0.18933340907096863, 0.2389327585697174, 0.13645797967910767, 0.17895153164863586, 0.13153888285160065, 0.18907344341278076, 0.15776272118091583, 0.12322942167520523, 0.11509858816862106, 0.14903919398784637, 0.18750949203968048, 0.16983361542224884, 0.1676577776670456, 0.14174525439739227, 0.16945388913154602, 0.11123037338256836, 0.10518544912338257, 0.1951732635498047, 0.23498301208019257, 0.11300748586654663, 0.096847303211689, 0.09012416750192642, 0.1630171686410904, 0.23125064373016357, 0.1786038875579834, 0.18219125270843506, 0.11858753859996796, 0.1416705846786499, 0.1345079243183136, 0.06540268659591675, 0.15037791430950165, 0.13326595723628998, 0.18607959151268005, 0.15247459709644318, 0.1941087245941162, 0.19624915719032288, 0.16005535423755646, 0.1267971396446228, 0.10581465810537338, 0.18762710690498352, 0.11707397550344467, 0.1514536738395691, 0.1303636133670807, 0.1635800451040268, 0.16410937905311584, 0.17009639739990234, 0.1263982206583023, 0.09098628908395767, 0.12508028745651245, 0.09905438125133514, 0.1351335644721985, 0.09356456249952316, 0.10686331242322922, 0.09372659772634506, 0.14921067655086517, 0.2361275553703308, 0.1761494278907776, 0.2053934931755066, 0.11347400397062302, 0.1363360732793808, 0.13565558195114136, 0.09139258414506912, 0.12228712439537048, 0.16131465137004852, 0.1637483388185501, 0.12599395215511322, 0.1893054097890854, 0.12103245407342911, 0.1980743408203125, 0.14174962043762207, 0.205588698387146, 0.18652379512786865, 0.20133155584335327, 0.152523010969162, 0.12732034921646118, 0.22039170563220978, 0.14478039741516113, 0.09851577877998352, 0.1878754198551178, 0.15559424459934235, 0.16079890727996826, 0.18553905189037323, 0.06771862506866455, 0.1510818600654602, 0.17619046568870544, 0.07524707913398743, 0.08606785535812378, 0.10663824528455734, 0.11158176511526108, 0.2012641429901123, 0.12193509191274643, 0.11876785010099411, 0.14273884892463684, 0.16954953968524933, 0.1350831240415573, 0.13737525045871735, 0.1781834363937378, 0.1268922984600067, 0.14645084738731384, 0.21310460567474365, 0.1862611025571823, 0.11411547660827637, 0.15748152136802673, 0.10930205136537552, 0.16073009371757507, 0.19375891983509064, 0.11941376328468323, 0.15834708511829376, 0.07797961682081223, 0.08822119235992432, 0.17054533958435059, 0.15790320932865143, 0.16020572185516357, 0.1883721500635147, 0.11864728480577469, 0.1332843154668808, 0.11387145519256592, 0.23628821969032288, 0.17529788613319397, 0.08138265460729599, 0.1678386628627777, 0.11618787795305252, 0.11113300174474716, 0.13317103683948517, 0.1475013792514801, 0.24304358661174774, 0.1739971935749054, 0.16725608706474304, 0.13373205065727234, 0.2364676296710968, 0.1325778216123581, 0.09629575163125992, 0.13205409049987793, 0.14655418694019318, 0.11842125654220581, 0.11432912200689316, 0.1444176435470581, 0.12297811359167099, 0.1252116560935974, 0.12921911478042603, 0.15534982085227966, 0.18631792068481445, 0.21961230039596558, 0.22115981578826904, 0.1636895388364792, 0.09834645688533783, 0.15683181583881378, 0.2000623345375061, 0.09013589471578598, 0.08459162712097168, 0.16496224701404572, 0.1935354322195053, 0.22308078408241272, 0.10970938205718994, 0.12433239072561264, 0.6116495132446289, 1.65127432346344, 1.3912965059280396, 1.7351734638214111, 0.8862316608428955, 1.3531994819641113, 1.1430816650390625, 1.0419174432754517, 2.3131463527679443, 1.0450880527496338, 0.7494267225265503, 0.9343968629837036, 1.1251378059387207, 0.6586271524429321, 1.1388264894485474, 0.8311670422554016, 1.6465773582458496, 1.2466157674789429, 0.7903469800949097, 0.9073759317398071, 0.8656085133552551, 0.8876480460166931, 0.8068286776542664, 1.2256540060043335, 1.0403101444244385, 0.7529722452163696, 1.1294970512390137, 0.5168380737304688, 0.9347652792930603, 1.1677967309951782, 0.7491649985313416, 1.2512397766113281, 0.7332528233528137, 1.016036033630371, 0.8308790326118469, 1.3791759014129639, 2.162733793258667, 1.3334863185882568, 0.9625403881072998, 0.6498342752456665, 0.7848922610282898, 1.1035113334655762, 0.7230324149131775, 0.556219756603241, 1.4585442543029785, 0.8248653411865234, 1.048863172531128, 1.2199856042861938, 1.0313048362731934, 1.0648272037506104, 0.7437856197357178, 1.117843747138977, 1.5177853107452393, 1.3357250690460205, 1.280247449874878, 1.3076528310775757, 0.9644486308097839, 1.5917446613311768, 1.0823674201965332, 0.9487935304641724, 0.6793235540390015, 1.1374436616897583, 1.079154372215271, 0.9413249492645264, 0.8372523188591003, 1.573081374168396, 2.36348295211792, 0.8886868357658386, 1.2147653102874756, 0.8462269306182861, 0.6514109373092651, 1.6285793781280518, 0.8679516911506653, 1.2265307903289795, 1.8933123350143433, 1.0405027866363525, 0.6796685457229614, 0.6236859560012817, 0.763445258140564, 0.7894110679626465, 0.6389237642288208, 0.6670463681221008, 1.3364057540893555, 0.929489254951477, 1.1939611434936523, 1.1780271530151367, 1.2389975786209106, 0.5978473424911499, 0.6841923594474792, 0.870660662651062, 0.9872733950614929, 0.913079023361206, 0.5581334829330444, 1.0018982887268066, 0.9145177006721497, 1.7383226156234741, 0.9921480417251587, 0.7299044728279114, 0.9764609336853027, 1.5486118793487549, 1.3233654499053955, 1.4042354822158813, 1.4569306373596191, 0.9486193060874939, 0.5670395493507385, 1.2217053174972534, 1.325162649154663, 1.2238166332244873, 1.4541040658950806, 1.3578041791915894, 1.2566533088684082, 0.5613438487052917, 1.0974184274673462, 1.6480642557144165, 0.6486776471138, 1.1795992851257324, 1.2544233798980713, 1.2980847358703613, 1.7782824039459229, 0.5890503525733948, 1.443575143814087, 1.0783565044403076, 1.2683961391448975, 0.8539603352546692, 0.9571835398674011, 0.6697978973388672, 0.9816889762878418, 0.7623232007026672, 1.1726468801498413, 1.6528939008712769, 1.1549530029296875, 0.5379489660263062, 0.6717281341552734, 1.382216453552246, 0.9923522472381592, 1.011263370513916, 0.8475394248962402, 0.6887106895446777, 1.1096827983856201, 1.281367301940918, 1.639695644378662, 1.1786926984786987, 0.9899167418479919, 0.8063987493515015, 1.0856093168258667, 0.6147176027297974, 0.601502537727356, 0.8636777997016907, 1.3553411960601807, 1.0249285697937012, 1.023144245147705, 1.4053781032562256, 0.7820664644241333, 0.7226288914680481, 0.9227709770202637, 1.4883654117584229, 1.1647731065750122, 1.0724165439605713, 0.4335918426513672, 1.0163230895996094, 1.2461134195327759, 1.2622787952423096, 0.8345808982849121, 1.6072832345962524, 1.239538311958313, 1.4025331735610962, 1.2681636810302734, 0.8169700503349304, 1.451620101928711, 1.2515161037445068, 0.82794189453125, 1.4229131937026978, 0.6680504679679871, 1.5630906820297241, 0.7949142456054688, 1.511417031288147, 1.6288622617721558, 1.6433013677597046, 1.6125789880752563, 0.8953964114189148, 0.7908819317817688, 0.909419059753418, 1.1583105325698853, 1.4705346822738647, 0.8412677049636841, 1.3110040426254272, 0.9476392865180969, 0.8976489305496216, 1.204875111579895, 1.6506004333496094, 1.2249338626861572, 0.8545212149620056, 0.7470949292182922, 0.43157482147216797, 0.8630087971687317, 1.0836771726608276, 0.8491390943527222, 1.0338656902313232, 1.130973219871521, 0.8119019865989685, 1.636400818824768, 1.4042574167251587, 1.6770119667053223, 1.482779860496521, 0.9761247038841248, 0.9193084239959717, 1.1950112581253052, 0.7911990284919739, 1.1460130214691162, 0.9381656646728516, 1.113576054573059, 0.8786676526069641, 0.6614745855331421, 1.4053007364273071, 1.0572566986083984, 0.9573685526847839, 0.9690009951591492, 1.4971656799316406, 1.2522599697113037, 1.3293243646621704, 1.2966651916503906, 1.1429342031478882, 0.704510509967804, 1.3046059608459473, 0.9231072664260864, 0.8265145421028137, 1.7858774662017822, 1.0375568866729736, 0.9821475148200989, 1.0291396379470825, 1.5693187713623047, 0.5498689413070679, 0.6528924703598022, 1.5156784057617188, 0.7443188428878784, 1.2131450176239014, 1.1841434240341187, 1.2326345443725586, 0.7350448966026306, 1.2940826416015625, 0.8869102001190186, 2.078005075454712, 0.5997532606124878, 1.6078283786773682, 1.1426196098327637, 1.3893400430679321, 0.9984760284423828, 1.474765419960022, 0.9790919423103333, 1.0491015911102295, 0.9999829530715942, 0.9147930145263672, 1.6868008375167847, 0.8803269267082214, 0.691259503364563, 0.7879462838172913, 0.7922682762145996, 2.502445697784424, 1.4324747323989868, 0.7994605898857117, 1.2167119979858398, 0.9772268533706665, 0.6572044491767883, 0.9492368698120117, 1.3967173099517822, 1.2402143478393555, 1.4637552499771118, 1.167297601699829, 0.7232502102851868, 1.2741680145263672, 1.3248584270477295, 0.6457798480987549, 1.24604332447052, 0.768914520740509, 0.6200870871543884, 1.1160948276519775, 1.537766695022583, 1.6016933917999268, 0.5260643362998962, 1.8860399723052979, 1.3562692403793335, 0.9953869581222534, 1.2234020233154297, 0.6298917531967163, 0.7261772751808167, 1.4414863586425781, 1.835541009902954, 1.5514822006225586, 0.9858248829841614, 1.6815801858901978, 1.300464153289795, 1.178407907485962, 1.8277848958969116, 1.026214838027954, 1.3028658628463745, 1.2420471906661987, 1.185669183731079, 1.1471151113510132, 1.9092031717300415, 1.3324044942855835, 56.55971145629883, 65.23487854003906, 21.527055740356445, 62.125732421875, 121.55435180664062, 145.03221130371094, 101.03631591796875, 97.1500015258789, 22.915922164916992, 113.9569320678711, 19.973468780517578, 83.67729949951172, 69.22411346435547, 131.4065704345703, 36.52492904663086, 31.9183349609375, 168.8035125732422, 53.75213623046875, 69.42849731445312, 137.646728515625, 133.7156982421875, 121.0651626586914, 45.29142379760742, 155.81153869628906, 29.224061965942383, 42.8455810546875, 82.80462646484375, 52.3997802734375, 62.26727294921875, 196.82254028320312, 23.20549774169922, 19.95880126953125, 108.64315795898438, 19.855636596679688, 86.55203247070312, 30.39697265625, 68.74247741699219, 94.8961181640625, 18.030057907104492, 134.5042724609375, 117.6123046875, 195.4380645751953, 45.66132354736328, 131.63385009765625, 111.38138580322266, 24.650663375854492, 132.71502685546875, 120.52654266357422, 123.67021942138672, 34.36330795288086, 83.38326263427734, 89.46566009521484, 132.4794158935547, 29.213134765625, 34.09075927734375, 34.09423828125, 45.75922775268555, 72.21758270263672, 89.01079559326172, 57.994384765625, 115.07533264160156, 24.155912399291992, 120.51505279541016, 79.66273498535156, 122.57596588134766, 163.16424560546875, 21.007165908813477, 172.5740966796875, 76.63626098632812, 85.7278823852539, 23.2403564453125, 78.09524536132812, 143.62200927734375, 46.60736083984375, 76.36385345458984, 127.7626953125, 98.91706848144531, 99.95162200927734, 62.16156005859375, 67.3603515625, 49.579925537109375, 100.40597534179688, 50.16995620727539, 110.1220703125, 38.834808349609375, 112.07280731201172, 47.35244369506836, 78.82305145263672, 133.7162628173828, 64.9911117553711, 59.62210464477539, 103.68509674072266, 39.34226608276367, 29.5977725982666, 34.94410705566406, 21.341102600097656, 107.71440887451172, 38.100677490234375, 33.270965576171875, 63.803504943847656, 134.04344177246094, 51.27700424194336, 86.86089324951172, 64.13434600830078, 122.771240234375, 65.9490966796875, 82.62965393066406, 131.02935791015625, 29.66644287109375, 73.29879760742188, 26.50656509399414, 148.38894653320312, 118.03105926513672, 116.79428100585938, 136.48880004882812, 86.76896667480469, 31.52886962890625, 104.36339569091797, 19.17437744140625, 63.548797607421875, 105.40789794921875, 32.360107421875, 74.47779846191406, 139.92404174804688, 35.586734771728516, 40.79399108886719, 118.13311004638672, 23.084228515625, 101.19205474853516, 23.157377243041992, 53.87721633911133, 45.03404235839844, 24.57904052734375, 59.1981315612793, 64.64846801757812, 114.633056640625, 23.146024703979492, 145.41064453125, 283.918701171875, 63.87759017944336, 84.77843475341797, 52.935115814208984, 69.98977661132812, 169.20046997070312, 58.363037109375, 72.6863784790039, 146.21597290039062, 120.39169311523438, 58.05926513671875, 76.22499084472656, 175.73106384277344, 44.37063217163086, 23.40824317932129, 49.67158126831055, 72.28695678710938, 51.42926788330078, 81.21324157714844, 37.97148513793945, 59.07952880859375, 85.84298706054688, 72.33905029296875, 53.102840423583984, 190.9130401611328, 71.35346221923828, 107.81678771972656, 36.3978271484375, 38.91802978515625, 93.91288757324219, 18.52484130859375, 203.07640075683594, 70.0923843383789, 32.201171875, 80.65911865234375, 107.47171783447266, 106.0033187866211, 119.3753662109375, 118.06195068359375, 124.55074310302734, 66.99461364746094, 47.71753692626953, 24.805145263671875, 43.05495071411133, 56.32366943359375, 100.931640625, 81.26138305664062, 20.8392333984375, 88.08768463134766, 206.44293212890625, 183.8749542236328, 28.78765869140625, 202.8955078125, 127.90581512451172, 187.63975524902344, 200.2010955810547, 141.50042724609375, 177.76622009277344, 24.374114990234375, 32.11155319213867, 15.992431640625, 210.9442138671875, 125.72705078125, 34.32283020019531, 127.63843536376953, 155.56637573242188, 215.87954711914062, 18.73297119140625, 128.47764587402344, 89.51714324951172, 212.5143280029297, 81.52264404296875, 119.89723205566406, 35.869850158691406, 47.617645263671875, 108.73163604736328, 127.19793701171875, 64.40635681152344, 92.41909790039062, 116.72186279296875, 93.923828125, 24.228729248046875, 67.60790252685547, 105.84029388427734, 58.26314163208008, 79.09966278076172, 67.81475067138672, 45.31154251098633, 19.20025634765625, 89.3378677368164, 146.54454040527344, 44.0425910949707, 116.90277099609375, 93.21240234375, 53.491943359375, 30.054534912109375, 27.73175048828125, 99.03787994384766, 110.16204833984375, 80.29840850830078, 71.23367309570312, 141.64495849609375, 123.39652252197266, 45.51513671875, 111.997314453125, 204.537841796875, 27.77949333190918, 77.50469207763672, 123.0750732421875, 81.4236831665039, 26.914457321166992, 73.68895721435547, 20.911527633666992, 16.99452018737793, 45.505653381347656, 151.35911560058594, 89.63499450683594, 224.0478057861328, 56.890472412109375, 157.79991149902344, 27.51370620727539, 36.47780990600586, 51.23877716064453, 121.01898193359375, 55.272117614746094, 97.7035903930664, 94.49787902832031, 119.00933074951172, 214.11590576171875, 152.7305450439453, 117.05033111572266, 190.7635040283203, 179.4373779296875, 19.596899032592773, 46.899383544921875, 20.12921142578125, 107.45069885253906, 16.51144790649414, 79.65857696533203, 59.40388488769531, 30.405336380004883, 227.22666931152344, 141.16929626464844, 24.7298583984375, 82.44976043701172, 159.97299194335938, 40.574058532714844, 24.904743194580078, 75.53073120117188, 155.4782257080078, 213.5927276611328, 125.31317138671875, 79.69964599609375, 40.086273193359375, 115.08544921875, 206.28436279296875, 195.7272186279297, 105.27191162109375, 99.880859375, 56.73780822753906, 29.69734764099121, 65.60604858398438, 1.6312743425369263, 2.368225574493408, 2.960782289505005, 2.161440849304199, 2.400326728820801, 2.2407796382904053, 2.7544915676116943, 2.6323578357696533, 2.6624655723571777, 1.6465080976486206, 1.752763271331787, 2.044408082962036, 1.7679922580718994, 2.227250337600708, 2.668630361557007, 2.4367547035217285, 1.3754509687423706, 1.8842763900756836, 3.2906124591827393, 2.5816683769226074, 2.260495185852051, 3.2814269065856934, 2.926107168197632, 1.191544532775879, 2.493001699447632, 2.249709129333496, 2.2164525985717773, 2.089604377746582, 2.4928295612335205, 2.216575860977173, 2.78716778755188, 2.020052909851074, 1.5749998092651367, 2.091695547103882, 2.3798646926879883, 1.9833077192306519, 1.949941635131836, 2.0066041946411133, 2.791539192199707, 2.182185173034668, 3.727928876876831, 2.694847345352173, 1.6485552787780762, 1.6523927450180054, 2.1000664234161377, 1.5560712814331055, 2.7467143535614014, 2.960252523422241, 1.978131651878357, 1.5732100009918213, 1.9635677337646484, 1.7430524826049805, 2.1739234924316406, 2.17380428314209, 2.407942533493042, 3.1846439838409424, 1.8725918531417847, 2.3389275074005127, 1.7301913499832153, 1.8321729898452759, 1.8032598495483398, 3.248067855834961, 2.9304580688476562, 2.645005464553833, 1.8656492233276367, 3.738922595977783, 2.6077163219451904, 2.041473388671875, 1.4151238203048706, 2.9186737537384033, 2.354119300842285, 3.155524730682373, 1.8419981002807617, 1.525191307067871, 3.3242673873901367, 2.3488190174102783, 2.963663339614868, 1.561521291732788, 1.9010246992111206, 1.3978080749511719, 3.0881588459014893, 3.357055187225342, 2.2178430557250977, 1.6154650449752808, 1.6541680097579956, 2.76511549949646, 3.0137147903442383, 2.200423002243042, 2.802635431289673, 2.9750213623046875, 1.8527573347091675, 1.7239488363265991, 2.1556615829467773, 2.1575381755828857, 1.6688205003738403, 2.7907965183258057, 3.049241304397583, 2.1744091510772705, 2.4222044944763184, 2.231411933898926, 2.886786699295044, 3.103945255279541, 1.6380033493041992, 3.122332811355591, 2.030463218688965, 1.5026766061782837, 1.0148000717163086, 2.3100006580352783, 2.0384912490844727, 2.465447425842285, 1.6998014450073242, 2.3984553813934326, 2.079379081726074, 1.290363073348999, 2.159703254699707, 2.628004789352417, 1.6877355575561523, 2.4470176696777344, 2.1818039417266846, 1.7339071035385132, 2.6646740436553955, 2.014843463897705, 2.1453213691711426, 1.584792137145996, 1.624123454093933, 3.0067391395568848, 1.9849576950073242, 3.1246113777160645, 2.1402227878570557, 2.4231581687927246, 1.6432218551635742, 1.334302544593811, 2.08272647857666, 2.1506223678588867, 2.6894257068634033, 1.7907116413116455, 2.9994654655456543, 3.760859489440918, 2.5807695388793945, 2.9028637409210205, 2.591883420944214, 3.040844678878784, 2.6440587043762207, 2.619891405105591, 1.7482308149337769, 3.485955238342285, 1.8512831926345825, 1.9291046857833862, 2.699786424636841, 2.5947539806365967, 3.050736665725708, 2.893609046936035, 2.8661911487579346, 3.366023540496826, 1.448571801185608, 2.2493648529052734, 3.310796022415161, 3.166499376296997, 1.7592438459396362, 2.4450063705444336, 1.5925474166870117, 3.1472551822662354, 1.785691499710083, 1.391724705696106, 3.3982326984405518, 1.8284239768981934, 2.3958775997161865, 2.6538031101226807, 1.4874237775802612, 2.39518141746521, 1.5672768354415894, 1.9223661422729492, 3.5298118591308594, 1.5441073179244995, 3.6698827743530273, 2.9875078201293945, 3.076552152633667, 1.5668286085128784, 1.9811842441558838, 1.8376878499984741, 2.006030321121216, 1.7873361110687256, 2.652207612991333, 1.8054571151733398, 2.416897773742676, 1.8710088729858398, 1.9079517126083374, 1.1905107498168945, 2.2473955154418945, 2.651608943939209, 3.555584669113159, 2.8650877475738525, 1.986378788948059, 2.346405029296875, 1.6799187660217285, 1.9307411909103394, 2.0350027084350586, 1.6983060836791992, 1.3884402513504028, 3.5542590618133545, 2.3104782104492188, 2.8094706535339355, 3.4192798137664795, 2.539149284362793, 3.199734926223755, 1.643699049949646, 2.769282817840576, 3.805955171585083, 3.2694501876831055, 3.2714226245880127, 1.899491548538208, 2.886946439743042, 2.5680761337280273, 2.606313467025757, 2.461298704147339, 2.0133049488067627, 2.4483742713928223, 1.8619686365127563, 1.9182004928588867, 2.1348471641540527, 1.6734017133712769, 2.158381700515747, 3.070910692214966, 2.566985607147217, 3.4245104789733887, 1.674226999282837, 2.432673215866089, 2.5887537002563477, 2.582394599914551, 3.565260648727417, 2.3980531692504883, 2.777400255203247, 2.5964441299438477, 1.0847254991531372, 2.922278881072998, 2.467005968093872, 2.2854223251342773, 1.5098333358764648, 2.021570920944214, 1.1657018661499023, 1.072190523147583, 2.7982914447784424, 2.210801124572754, 1.7594366073608398, 2.058746337890625, 2.4352333545684814, 3.088763475418091, 1.4142831563949585, 2.3353681564331055, 2.8626022338867188, 2.024923324584961, 3.224883556365967, 1.680331826210022, 2.7117269039154053, 1.440126657485962, 2.4671332836151123, 2.27276873588562, 2.580792188644409, 2.90928316116333, 2.834343910217285, 1.747139811515808, 2.807745933532715, 2.6410205364227295, 2.86684513092041, 3.0984721183776855, 1.997315526008606, 1.3568733930587769, 1.2291555404663086, 3.2653074264526367, 2.2522244453430176, 2.0784997940063477, 2.0975847244262695, 2.68247127532959, 1.2515381574630737, 1.505086064338684, 2.381019115447998, 2.4895007610321045, 1.9697619676589966, 2.7646031379699707, 1.7790545225143433, 2.173344135284424, 2.909881591796875, 2.818476915359497, 3.2571141719818115, 3.08719539642334, 2.4423513412475586, 1.873883605003357, 1.5562314987182617, 2.691180467605591, 2.0951900482177734, 3.501694917678833, 2.5040292739868164, 2.1266391277313232, 4.198885917663574, 3.3043038845062256, 1.6715213060379028, 1.9167627096176147, 3.0050158500671387, 2.567014455795288, 1.467677116394043, 0.14210361242294312, 0.16269725561141968, 0.16955213248729706, 0.20069848001003265, 0.19966033101081848, 0.1733839064836502, 0.19428187608718872, 0.18495841324329376, 0.18973910808563232, 0.12059560418128967, 0.19115421175956726, 0.1265406608581543, 0.17942363023757935, 0.19620098173618317, 0.11326722800731659, 0.16246947646141052, 0.1299683004617691, 0.12812484800815582, 0.1365528404712677, 0.10748070478439331, 0.1559402495622635, 0.1511470526456833, 0.1819189339876175, 0.1370944380760193, 0.17577096819877625, 0.17137248814105988, 0.2183120995759964, 0.16141924262046814, 0.1629345715045929, 0.16260497272014618, 0.20231236517429352, 0.11453630030155182, 0.1715189665555954, 0.12424487620592117, 0.15070748329162598, 0.12070105224847794, 0.18127425014972687, 0.23445871472358704, 0.17931528389453888, 0.1281137615442276, 0.21930022537708282, 0.12673792243003845, 0.1404576152563095, 0.09038424491882324, 0.15351985394954681, 0.12360458821058273, 0.12686371803283691, 0.21928167343139648, 0.17684711515903473, 0.20998990535736084, 0.15094098448753357, 0.11335823684930801, 0.1813346892595291, 0.14185985922813416, 0.19247116148471832, 0.08007317036390305, 0.18604020774364471, 0.1812845766544342, 0.15335820615291595, 0.23832103610038757, 0.21667037904262543, 0.1464906483888626, 0.15026284754276276, 0.20902888476848602, 0.13693611323833466, 0.12028296291828156, 0.14224469661712646, 0.17463591694831848, 0.10802806913852692, 0.11766308546066284, 0.11578056216239929, 0.11777974665164948, 0.14038509130477905, 0.12746502459049225, 0.1274726390838623, 0.17533862590789795, 0.11298087984323502, 0.18794122338294983, 0.2409810572862625, 0.10927578806877136, 0.20190969109535217, 0.1847842037677765, 0.1534872055053711, 0.09654288738965988, 0.2094503790140152, 0.11892993003129959, 0.14084279537200928, 0.16186878085136414, 0.13465414941310883, 0.21647591888904572, 0.1721876859664917, 0.14366966485977173, 0.06354615837335587, 0.10751084983348846, 0.14443089067935944, 0.1428380310535431, 0.16542184352874756, 0.13278013467788696, 0.1681002825498581, 0.11923444271087646, 0.11730285733938217, 0.20367945730686188, 0.24381469190120697, 0.17424209415912628, 0.1617785543203354, 0.12340433895587921, 0.11488618701696396, 0.1368829756975174, 0.14491841197013855, 0.17198534309864044, 0.16859667003154755, 0.17709071934223175, 0.12794189155101776, 0.1666080802679062, 0.12715183198451996, 0.18883174657821655, 0.11716873198747635, 0.17640578746795654, 0.23576410114765167, 0.12215202301740646, 0.1548941731452942, 0.20291514694690704, 0.17163966596126556, 0.13168193399906158, 0.13914179801940918, 0.16780853271484375, 0.1501808911561966, 0.24129748344421387, 0.10634923726320267, 0.18842162191867828, 0.18781161308288574, 0.09716962277889252, 0.17263126373291016, 0.15620099008083344, 0.12112236768007278, 0.15185745060443878, 0.10128587484359741, 0.18115080893039703, 0.18728259205818176, 0.12546446919441223, 0.10770845413208008, 0.15618367493152618, 0.1825009435415268, 0.09432017803192139, 0.12546426057815552, 0.11911436915397644, 0.20435211062431335, 0.15087272226810455, 0.1657588928937912, 0.1882232427597046, 0.2241804003715515, 0.11762317270040512, 0.1777363121509552, 0.146445631980896, 0.15516206622123718, 0.13033930957317352, 0.15668046474456787, 0.11924122273921967, 0.1457640528678894, 0.09908268600702286, 0.1460760533809662, 0.13758565485477448, 0.13126210868358612, 0.16523060202598572, 0.12339460849761963, 0.1735115349292755, 0.16726677119731903, 0.1392831802368164, 0.20272047817707062, 0.12186333537101746, 0.23690350353717804, 0.17389924824237823, 0.13382931053638458, 0.10865896195173264, 0.14767298102378845, 0.1701372116804123, 0.1655569225549698, 0.17313942313194275, 0.11754220724105835, 0.11419226974248886, 0.1146831288933754, 0.1852116733789444, 0.1606951504945755, 0.23659944534301758, 0.1733786016702652, 0.1100788488984108, 0.09928502142429352, 0.18307407200336456, 0.16276369988918304, 0.18721087276935577, 0.14566336572170258, 0.18796446919441223, 0.16012519598007202, 0.195632204413414, 0.12130828946828842, 0.1590028703212738, 0.15803241729736328, 0.1660015881061554, 0.13894417881965637, 0.20461511611938477, 0.15400433540344238, 0.16206179559230804, 0.15093614161014557, 0.1664894074201584, 0.14261145889759064, 0.23389308154582977, 0.15832313895225525, 0.17828907072544098, 0.11112258583307266, 0.18851310014724731, 0.18885484337806702, 0.18858186900615692, 0.17364566028118134, 0.0787508487701416, 0.10778618603944778, 0.1148802861571312, 0.14926238358020782, 0.1249314695596695, 0.1770745813846588, 0.11972755193710327, 0.05435162037611008, 0.21307292580604553, 0.1748970001935959, 0.24335721135139465, 0.16418476402759552, 0.1510327160358429, 0.11955322325229645, 0.0767941102385521, 0.1593172401189804, 0.1272527575492859, 0.14334462583065033, 0.14401867985725403, 0.1317981630563736, 0.1685205101966858, 0.0921396017074585, 0.14947618544101715, 0.10949007421731949, 0.11757422983646393, 0.17033210396766663, 0.10111583769321442, 0.22288788855075836, 0.15136155486106873, 0.10911553353071213, 0.1578635722398758, 0.16115045547485352, 0.17977961897850037, 0.12886463105678558, 0.15212631225585938, 0.13165561854839325, 0.16733264923095703, 0.1029471680521965, 0.1179676428437233, 0.2000742256641388, 0.145218163728714, 0.07037622481584549, 0.11125033348798752, 0.16109146177768707, 0.19907653331756592, 0.16776983439922333, 0.16897960007190704, 0.16448397934436798, 0.17504790425300598, 0.1609845757484436, 0.10431989282369614, 0.1737091839313507, 0.10630568861961365, 0.09291434288024902, 0.22369490563869476, 0.05902159959077835, 0.21346263587474823, 0.11436164379119873, 0.12356681376695633, 0.16968680918216705, 0.19871214032173157, 0.1625831127166748, 0.23065970838069916, 0.11342322826385498, 0.18105833232402802, 0.1092943623661995, 0.18816593289375305, 0.17540603876113892, 0.17069914937019348, 0.1807941049337387, 0.12608736753463745, 0.08518767356872559, 0.11915735900402069, 0.1803358793258667, 0.1206219419836998, 0.2216254323720932, 0.12495318800210953, 0.13988707959651947, 0.10880297422409058, 0.15297138690948486, 0.1557772159576416, 0.20169778168201447, 0.1334259957075119, 0.1306651532649994, 0.10543707758188248, 0.18816274404525757, 0.11445511877536774, 1.6149896383285522, 1.3990392684936523, 1.1322741508483887, 0.99869704246521, 0.8063888549804688, 1.0841164588928223, 1.3589611053466797, 1.432943344116211, 1.4672425985336304, 1.1276503801345825, 0.6930446624755859, 0.974543035030365, 1.070815086364746, 1.2105060815811157, 1.2666900157928467, 0.7931063771247864, 1.0708496570587158, 1.0652141571044922, 1.5679641962051392, 0.9310097098350525, 1.2592380046844482, 0.8244372606277466, 0.8577031493186951, 1.1165002584457397, 0.6051491498947144, 0.8988640904426575, 0.7325930595397949, 1.4829086065292358, 1.0983104705810547, 1.5499244928359985, 1.2242368459701538, 1.5455902814865112, 0.7046247720718384, 1.053367018699646, 0.8106133341789246, 1.8014816045761108, 1.2834911346435547, 1.1736212968826294, 0.9583593606948853, 0.7401314973831177, 1.3373574018478394, 0.9831271171569824, 1.134737491607666, 1.3278206586837769, 1.1061172485351562, 1.3841619491577148, 0.9119035005569458, 1.1461067199707031, 1.1391777992248535, 0.7071579098701477, 1.0411608219146729, 1.9555329084396362, 2.175863265991211, 0.9644569754600525, 0.7186723947525024, 1.2675153017044067, 1.1241118907928467, 0.7756416201591492, 0.8648942112922668, 0.8690881133079529, 0.8197537660598755, 0.9006693959236145, 1.1510926485061646, 0.6544061899185181, 0.7773032188415527, 0.944760799407959, 0.7792237401008606, 1.1289925575256348, 1.6140679121017456, 0.7688286900520325, 0.6922487020492554, 1.2345901727676392, 0.9139333963394165, 0.6754223704338074, 1.4277797937393188, 1.8296035528182983, 1.2875902652740479, 0.6943533420562744, 0.8183091282844543, 1.5292249917984009, 1.2248497009277344, 1.4430118799209595, 0.9417336583137512, 1.5241520404815674, 0.6796771287918091, 1.1476069688796997, 0.8351508975028992, 0.5741043090820312, 0.7446975708007812, 0.6728175282478333, 2.0510916709899902, 0.9527917504310608, 1.398876428604126, 1.1778662204742432, 1.46609365940094, 1.1020197868347168, 0.9239298105239868, 0.8925251364707947, 0.9370415806770325, 1.0623302459716797, 1.402793288230896, 1.0635433197021484, 0.5465810298919678, 0.8021076917648315, 1.738218903541565, 0.7881231307983398, 0.7244160175323486, 0.8579773306846619, 1.2178187370300293, 1.1827441453933716, 1.6031996011734009, 1.0468310117721558, 1.1974339485168457, 1.231406569480896, 0.9565372467041016, 0.9310401082038879, 0.9804710745811462, 1.2315523624420166, 1.3145971298217773, 1.194173812866211, 1.094320297241211, 1.1730973720550537, 1.4607053995132446, 0.9848469495773315, 1.6513042449951172, 1.3292614221572876, 1.4579658508300781, 0.8631010055541992, 1.294752836227417, 1.2878426313400269, 1.271538496017456, 1.16847562789917, 1.3917367458343506, 0.9155519008636475, 0.7199530601501465, 1.6785110235214233, 1.4896007776260376, 1.716199278831482, 1.21720552444458, 1.0356528759002686, 1.6153913736343384, 1.1605826616287231, 0.754993736743927, 1.213228702545166, 1.0213059186935425, 1.5968732833862305, 1.6549993753433228, 1.6822216510772705, 1.8069483041763306, 1.5122774839401245, 0.5511908531188965, 0.6178432106971741, 1.8872894048690796, 0.9743439555168152, 0.7089241147041321, 1.0730090141296387, 1.1561199426651, 1.1867070198059082, 1.9451398849487305, 0.5929372310638428, 1.15659499168396, 1.6831814050674438, 1.4817920923233032, 1.2906408309936523, 0.9988853335380554, 1.1202001571655273, 0.9798205494880676, 0.5952000021934509, 0.8631315231323242, 1.2228002548217773, 1.3604806661605835, 1.6465096473693848, 1.6721880435943604, 0.940546452999115, 0.9045910239219666, 0.6943447589874268, 1.3018845319747925, 0.7238842844963074, 1.5751116275787354, 1.222686529159546, 1.4014208316802979, 1.8957093954086304, 0.9374958872795105, 1.8810834884643555, 0.7362117767333984, 1.1335160732269287, 1.0385652780532837, 1.309354543685913, 1.3008149862289429, 1.8569329977035522, 0.8832422494888306, 1.0396801233291626, 0.9021822810173035, 2.3119587898254395, 0.9883443117141724, 1.0302671194076538, 1.2493828535079956, 1.0509918928146362, 0.37600523233413696, 1.1872531175613403, 1.081673264503479, 0.45583608746528625, 0.8753100633621216, 0.9879615306854248, 1.3056048154830933, 1.5109310150146484, 1.5054107904434204, 0.8800236582756042, 1.2101576328277588, 0.765480637550354, 2.0359530448913574, 0.9822105765342712, 1.136110544204712, 1.4274697303771973, 2.073310136795044, 1.3530642986297607, 1.7771424055099487, 1.7542122602462769, 1.1134722232818604, 1.2011218070983887, 2.062631845474243, 1.297394037246704, 1.2849377393722534, 0.865977942943573, 1.1495836973190308, 1.2856085300445557, 1.1911669969558716, 1.2130783796310425, 0.9169398546218872, 1.1009948253631592, 1.549075722694397, 1.2927420139312744, 1.2614781856536865, 1.0656065940856934, 1.3829374313354492, 0.70774245262146, 1.1063435077667236, 1.0739670991897583, 1.0567537546157837, 1.2831921577453613, 1.1445677280426025, 1.7336944341659546, 1.0639485120773315, 0.9230584502220154, 0.9100727438926697, 1.3330438137054443, 1.153280258178711, 1.3333572149276733, 1.2389267683029175, 1.7702759504318237, 1.1417559385299683, 1.2284338474273682, 1.3217867612838745, 1.3166521787643433, 0.8583353161811829, 0.6725627183914185, 1.1396915912628174, 1.4062546491622925, 1.0361063480377197, 1.1072767972946167, 0.8142693638801575, 0.6759624481201172, 1.4437615871429443, 1.0074001550674438, 1.2195883989334106, 1.2130529880523682, 1.2667268514633179, 1.6373181343078613, 1.0888235569000244, 2.115994453430176, 1.0682203769683838, 0.8394306898117065, 1.3674261569976807, 0.8847214579582214, 0.9192070364952087, 1.0396194458007812, 1.0081309080123901, 1.311386227607727, 1.7223349809646606, 1.4961515665054321, 1.6352752447128296, 0.6287565231323242, 1.1928030252456665, 1.2198662757873535, 1.163320541381836, 1.23558509349823, 1.6239150762557983, 0.8119229078292847, 1.4919826984405518, 1.0624167919158936, 1.3468351364135742, 0.8873632550239563, 0.9562902450561523, 0.6998047232627869, 1.3159188032150269, 1.5647491216659546, 0.9559128880500793, 0.9786351323127747, 0.642099142074585, 1.6951572895050049, 26.555665969848633, 80.71746826171875, 80.52877044677734, 144.89453125, 126.82280731201172, 86.29244232177734, 27.065277099609375, 29.44996452331543, 39.90322494506836, 254.80535888671875, 54.82178497314453, 138.9140625, 30.21304702758789, 43.199676513671875, 109.38372802734375, 110.35796356201172, 32.91660690307617, 83.89383697509766, 25.166532516479492, 41.90358352661133, 130.74485778808594, 96.1112060546875, 110.74351501464844, 99.34375, 100.85018157958984, 113.45263671875, 81.68682098388672, 39.07870864868164, 63.1925048828125, 40.43841552734375, 135.00762939453125, 86.63976287841797, 31.754150390625, 107.92508697509766, 94.16387176513672, 109.53105926513672, 46.2208251953125, 139.10694885253906, 76.70573425292969, 85.3226547241211, 71.45624542236328, 63.12849426269531, 39.41176986694336, 21.520263671875, 47.042816162109375, 44.61013412475586, 19.38165283203125, 27.37604522705078, 79.29411315917969, 99.07275390625, 49.441162109375, 75.43999481201172, 33.261474609375, 85.45915222167969, 60.71466064453125, 21.39784812927246, 85.82157135009766, 37.86492919921875, 31.1920166015625, 31.09222984313965, 65.1518325805664, 44.982547760009766, 58.49892807006836, 94.32554626464844, 51.88187026977539, 131.62286376953125, 21.2762451171875, 173.307373046875, 35.135581970214844, 156.80392456054688, 146.9102783203125, 131.02989196777344, 53.12811279296875, 19.27706527709961, 104.20419311523438, 45.97065353393555, 60.854793548583984, 38.72655487060547, 30.896398544311523, 57.984130859375, 68.46538543701172, 25.95452880859375, 108.05308532714844, 25.776702880859375, 151.5950927734375, 40.112030029296875, 45.89892578125, 52.8106689453125, 157.0008544921875, 54.99310302734375, 57.673828125, 87.18389129638672, 72.32879638671875, 163.078369140625, 112.29461669921875, 33.05060577392578, 162.54718017578125, 46.01750946044922, 65.26545715332031, 91.50450897216797, 86.21598815917969, 81.447265625, 129.6361083984375, 170.50762939453125, 62.17742919921875, 22.257596969604492, 65.76451873779297, 70.98013305664062, 33.35828399658203, 144.45994567871094, 25.06146240234375, 148.99642944335938, 100.56206512451172, 124.1805419921875, 65.09043884277344, 45.490203857421875, 125.51509857177734, 52.897705078125, 29.78228759765625, 143.23590087890625, 20.521303176879883, 224.6170654296875, 51.96438217163086, 47.09015655517578, 85.92201232910156, 104.42435455322266, 34.37396240234375, 20.23974609375, 129.99420166015625, 54.534149169921875, 89.43863677978516, 234.01670837402344, 75.9947509765625, 20.742523193359375, 111.58051300048828, 58.309417724609375, 67.84697723388672, 24.69989013671875, 62.77522277832031, 28.6962833404541, 141.10882568359375, 184.7519073486328, 63.577362060546875, 47.15291976928711, 70.55630493164062, 80.55489349365234, 109.83695220947266, 246.604248046875, 31.1448974609375, 103.63179779052734, 25.60096549987793, 140.38137817382812, 89.35183715820312, 180.0116424560547, 218.81260681152344, 104.5655517578125, 28.341501235961914, 84.87972259521484, 91.67534637451172, 28.676259994506836, 66.56329345703125, 66.13013458251953, 116.47186279296875, 61.91888427734375, 57.254886627197266, 35.8094482421875, 19.11578369140625, 114.7413558959961, 67.88705444335938, 94.93247985839844, 48.57429122924805, 288.08062744140625, 75.99614715576172, 101.9277114868164, 135.89483642578125, 89.18513488769531, 62.36957931518555, 82.98114013671875, 142.2265625, 160.309814453125, 161.7269287109375, 46.35011672973633, 124.678466796875, 153.25209045410156, 94.63335418701172, 98.945068359375, 88.8476333618164, 80.7239990234375, 103.99214935302734, 126.16616821289062, 30.65148162841797, 83.6673583984375, 64.63994598388672, 84.5234146118164, 127.61568450927734, 45.6942138671875, 27.151166915893555, 36.96805953979492, 24.009857177734375, 93.786865234375, 56.486873626708984, 155.6872100830078, 75.83671569824219, 29.0200252532959, 121.69339752197266, 146.00466918945312, 130.587890625, 23.975526809692383, 40.72465515136719, 26.0113525390625, 19.667741775512695, 42.454803466796875, 90.02690887451172, 175.7904052734375, 25.543073654174805, 34.71460723876953, 22.923141479492188, 70.31851196289062, 47.44952392578125, 84.87625122070312, 88.06868743896484, 66.06867980957031, 89.26641082763672, 92.30400848388672, 114.45755767822266, 138.23159790039062, 26.881759643554688, 218.83905029296875, 185.960693359375, 68.02072143554688, 120.37030029296875, 85.87710571289062, 45.65119934082031, 294.55804443359375, 106.4050064086914, 72.42816162109375, 203.8203887939453, 57.47402572631836, 153.4755859375, 20.48980712890625, 151.28146362304688, 143.67352294921875, 72.10574340820312, 50.258636474609375, 53.852210998535156, 211.38780212402344, 37.16933822631836, 184.0772247314453, 161.58917236328125, 39.13018798828125, 135.44305419921875, 45.12226486206055, 113.31108856201172, 38.062744140625, 25.528182983398438, 178.09915161132812, 67.80168151855469, 250.8676300048828, 141.31939697265625, 42.127479553222656, 22.307111740112305, 59.1292724609375, 84.53042602539062, 166.076904296875, 251.86827087402344, 23.747772216796875, 72.66313934326172, 167.75218200683594, 58.9886474609375, 50.39443588256836, 22.885223388671875, 68.48259735107422, 120.89154052734375, 39.3123779296875, 149.0418701171875, 103.21591186523438, 101.93448638916016, 121.36486053466797, 71.23544311523438, 41.789119720458984, 29.19256591796875, 45.08842849731445, 34.06710433959961, 22.554718017578125, 44.099910736083984, 77.49931335449219, 76.48426818847656, 111.3280258178711, 26.582773208618164, 45.87947082519531, 43.19208526611328, 31.332889556884766, 22.784940719604492, 143.94712829589844, 72.41316223144531, 65.84611511230469, 38.02261734008789, 30.88922119140625, 118.48577880859375, 50.24756622314453, 2.715963125228882, 3.0313501358032227, 1.143935203552246, 3.2049131393432617, 2.407711982727051, 3.206686019897461, 1.1124523878097534, 2.4421820640563965, 2.1259384155273438, 1.696526288986206, 2.4874141216278076, 2.1136395931243896, 2.3033745288848877, 2.505120277404785, 2.4460272789001465, 1.5696099996566772, 3.233715534210205, 1.4763497114181519, 3.655306816101074, 3.3489367961883545, 1.8927162885665894, 2.675490617752075, 1.2995665073394775, 3.0559005737304688, 1.6732406616210938, 2.4579391479492188, 2.049021005630493, 2.8835437297821045, 2.603288173675537, 2.196040391921997, 1.8793809413909912, 1.803365707397461, 2.6621971130371094, 1.903281807899475, 2.33072829246521, 4.147536277770996, 2.310960531234741, 2.5628631114959717, 2.5833702087402344, 2.1080827713012695, 2.3112688064575195, 2.316058397293091, 2.379427671432495, 2.4497711658477783, 3.39298939704895, 1.7611321210861206, 1.5586347579956055, 2.4353537559509277, 2.9664201736450195, 1.7207916975021362, 2.2334179878234863, 2.4860708713531494, 1.7440117597579956, 2.8530735969543457, 2.247239589691162, 1.9675605297088623, 1.7534513473510742, 1.4577093124389648, 2.508519172668457, 2.0580191612243652, 2.2956206798553467, 2.0570287704467773, 1.2171649932861328, 2.823939085006714, 2.884211301803589, 1.2509946823120117, 2.165787696838379, 2.2779464721679688, 3.2916975021362305, 1.6085240840911865, 2.595202684402466, 2.3695123195648193, 2.155217170715332, 1.5563087463378906, 1.0312553644180298, 1.8328880071640015, 2.644608974456787, 2.724749803543091, 1.9861491918563843, 2.8372936248779297, 2.769298553466797, 2.2803280353546143, 2.041295051574707, 1.808846354484558, 2.925908088684082, 3.2569568157196045, 1.9236797094345093, 1.1032570600509644, 2.3895423412323, 1.4734951257705688, 2.139002799987793, 1.769708514213562, 2.3157942295074463, 2.739081382751465, 2.247424840927124, 3.0212676525115967, 2.245547294616699, 2.9782605171203613, 3.369769811630249, 3.7678539752960205, 1.5195293426513672, 2.113297462463379, 2.4701220989227295, 2.2485923767089844, 1.7018013000488281, 2.5616326332092285, 2.526766061782837, 2.7404561042785645, 1.7993439435958862, 1.7828501462936401, 1.5131573677062988, 2.087357521057129, 2.823096513748169, 2.404071569442749, 1.9322428703308105, 1.840191125869751, 2.207463264465332, 3.5090062618255615, 1.434467077255249, 3.32836651802063, 2.8767178058624268, 3.213189125061035, 2.9850268363952637, 1.0855178833007812, 1.9422736167907715, 2.4884588718414307, 3.1149322986602783, 2.7464189529418945, 1.8032397031784058, 2.2578063011169434, 1.7593803405761719, 3.1159863471984863, 2.340017080307007, 2.107785224914551, 1.309975266456604, 2.172621488571167, 1.6063202619552612, 2.5065553188323975, 2.072089195251465, 2.1135780811309814, 3.138509511947632, 2.925438404083252, 3.5768589973449707, 2.2907934188842773, 1.5711631774902344, 1.4068554639816284, 2.9114925861358643, 2.970710039138794, 2.793459177017212, 1.9083503484725952, 2.5096940994262695, 1.4891250133514404, 1.7609548568725586, 1.9615812301635742, 2.2678728103637695, 3.115177631378174, 2.179224967956543, 3.425715923309326, 1.146535873413086, 2.1799135208129883, 2.1972525119781494, 2.1189966201782227, 2.9245083332061768, 2.6987578868865967, 2.2441647052764893, 2.584852457046509, 2.573730945587158, 2.0135183334350586, 2.4112908840179443, 3.080976724624634, 3.22031307220459, 2.7751359939575195, 1.735726237297058, 3.530801296234131, 3.121493101119995, 2.7668755054473877, 1.2419594526290894, 2.8743090629577637, 1.0311782360076904, 2.7013421058654785, 2.649667978286743, 3.4277734756469727, 1.8791401386260986, 2.980891466140747, 4.070742607116699, 1.998091697692871, 3.642761707305908, 1.6545891761779785, 2.3708410263061523, 2.008707284927368, 2.438462257385254, 2.0416300296783447, 2.9024901390075684, 2.049455404281616, 1.6814194917678833, 2.02834415435791, 2.96354603767395, 1.7808159589767456, 2.5435571670532227, 2.3769073486328125, 2.735452175140381, 2.686380624771118, 3.3983640670776367, 2.269585609436035, 3.4355645179748535, 2.6103298664093018, 2.282029151916504, 1.6813095808029175, 2.4489200115203857, 1.7929848432540894, 1.2001982927322388, 3.119659662246704, 2.358250617980957, 3.5763354301452637, 3.0203163623809814, 1.4026949405670166, 2.6640961170196533, 2.826939821243286, 2.409562110900879, 2.503276824951172, 1.7793742418289185, 1.588742971420288, 2.6494407653808594, 2.5734987258911133, 3.1003973484039307, 1.4777926206588745, 3.519148588180542, 2.7473480701446533, 2.564135789871216, 2.302436590194702, 1.4636690616607666, 3.117194175720215, 2.618070602416992, 2.1029844284057617, 2.78295636177063, 3.4146037101745605, 3.2136125564575195, 2.2445175647735596, 2.3156027793884277, 1.8488510847091675, 1.8818333148956299, 1.5544309616088867, 1.525801658630371, 3.2656755447387695, 3.358405113220215, 1.9362701177597046, 2.9101507663726807, 1.9908312559127808, 3.0441734790802, 2.138258934020996, 1.7971093654632568, 2.0128393173217773, 2.6214141845703125, 2.5907928943634033, 1.924282431602478, 1.7866355180740356, 2.5332019329071045, 2.3399438858032227, 2.9844648838043213, 2.273392915725708, 2.048602342605591, 2.361182451248169, 2.4334824085235596, 2.7054240703582764, 2.3931198120117188, 2.667523145675659, 1.6934690475463867, 2.4241671562194824, 3.7921111583709717, 1.7973204851150513, 1.7308684587478638, 2.3756656646728516, 3.374980926513672, 2.7136058807373047, 1.1744542121887207, 3.4998698234558105, 2.467100143432617, 3.2301816940307617, 3.4005115032196045, 2.2295541763305664, 4.164996147155762, 2.43542742729187, 2.696594715118408, 1.2485814094543457, 2.3935277462005615, 3.771437406539917, 1.3104902505874634, 1.831655502319336, 3.7246274948120117, 1.6643552780151367, 3.9413058757781982, 2.2294607162475586, 2.1722002029418945, 1.599712610244751, 2.063291311264038, 2.808781147003174, 2.2847647666931152, 3.0650875568389893, 2.503649950027466, 2.4241838455200195, 0.17154239118099213, 0.14738239347934723, 0.20161014795303345, 0.16554957628250122, 0.20297963917255402, 0.15525293350219727, 0.14333336055278778, 0.16848522424697876, 0.15739454329013824, 0.1289377063512802, 0.11557622998952866, 0.19544079899787903, 0.21046696603298187, 0.1543102264404297, 0.1463049054145813, 0.23362837731838226, 0.16389602422714233, 0.1903761625289917, 0.16208842396736145, 0.1672997623682022, 0.11238373816013336, 0.11634160578250885, 0.18864946067333221, 0.15230709314346313, 0.140322744846344, 0.09035798907279968, 0.16378867626190186, 0.14539501070976257, 0.1622779816389084, 0.11514369398355484, 0.10324724018573761, 0.17988009750843048, 0.23779235780239105, 0.13412784039974213, 0.0990607887506485, 0.14863520860671997, 0.14123381674289703, 0.1809149831533432, 0.10723932087421417, 0.1855800598859787, 0.11580764502286911, 0.17242200672626495, 0.20893287658691406, 0.07358404994010925, 0.1909005343914032, 0.19979983568191528, 0.19616736471652985, 0.1066790297627449, 0.14243583381175995, 0.13315175473690033, 0.1884993314743042, 0.10758331418037415, 0.18816426396369934, 0.14761902391910553, 0.12626007199287415, 0.16871888935565948, 0.15036359429359436, 0.11629712581634521, 0.1556173712015152, 0.13279035687446594, 0.14461129903793335, 0.19547690451145172, 0.11691121757030487, 0.17609503865242004, 0.08122999221086502, 0.11359041184186935, 0.1371103823184967, 0.15906056761741638, 0.12584853172302246, 0.09690262377262115, 0.09870930761098862, 0.09542331844568253, 0.17166446149349213, 0.10150396078824997, 0.13183650374412537, 0.10590509325265884, 0.13908511400222778, 0.2371513843536377, 0.197615385055542, 0.22206524014472961, 0.2200288027524948, 0.15685495734214783, 0.12979863584041595, 0.1620764136314392, 0.16125835478305817, 0.1963619738817215, 0.17830447852611542, 0.11852826923131943, 0.18940246105194092, 0.14359715580940247, 0.1927676796913147, 0.19404734671115875, 0.19235484302043915, 0.18236838281154633, 0.09647277742624283, 0.2093231976032257, 0.1339259147644043, 0.08231708407402039, 0.18264105916023254, 0.14658226072788239, 0.19214189052581787, 0.0993758961558342, 0.09187518805265427, 0.114781454205513, 0.16635791957378387, 0.14172056317329407, 0.15620246529579163, 0.10256002098321915, 0.16421416401863098, 0.16556476056575775, 0.11313959211111069, 0.18182314932346344, 0.15177972614765167, 0.17494626343250275, 0.11301800608634949, 0.23838350176811218, 0.1272846758365631, 0.15045136213302612, 0.10836194455623627, 0.10087326169013977, 0.08161062002182007, 0.09267419576644897, 0.10739877820014954, 0.15602755546569824, 0.11978941410779953, 0.18172530829906464, 0.1174435019493103, 0.15601897239685059, 0.11215193569660187, 0.1274031102657318, 0.19252021610736847, 0.16817732155323029, 0.21303947269916534, 0.14314258098602295, 0.15186482667922974, 0.1989181786775589, 0.17714646458625793, 0.09371867775917053, 0.11210192739963531, 0.18263041973114014, 0.09474339336156845, 0.12941737473011017, 0.13919401168823242, 0.1296909600496292, 0.1087488904595375, 0.12636971473693848, 0.13836915791034698, 0.18416431546211243, 0.0895691066980362, 0.1461661159992218, 0.13564875721931458, 0.194691464304924, 0.2352249026298523, 0.1343313604593277, 0.10869663953781128, 0.112797312438488, 0.22196048498153687, 0.1291724592447281, 0.16049443185329437, 0.16360782086849213, 0.14853912591934204, 0.16737350821495056, 0.18728625774383545, 0.1969093233346939, 0.1707209348678589, 0.18909484148025513, 0.11576694995164871, 0.17308638989925385, 0.1758652776479721, 0.1157306432723999, 0.17740745842456818, 0.1957520991563797, 0.19285328686237335, 0.14943496882915497, 0.10003972798585892, 0.08305052667856216, 0.16279160976409912, 0.10801368206739426, 0.18563102185726166, 0.17657470703125, 0.18351878225803375, 0.17485196888446808, 0.14118032157421112, 0.07350671291351318, 0.15489883720874786, 0.12709693610668182, 0.1605772227048874, 0.13864463567733765, 0.21377038955688477, 0.12858594954013824, 0.09637479484081268, 0.14424943923950195, 0.17912657558918, 0.10400886088609695, 0.12862130999565125, 0.10121356695890427, 0.11028242111206055, 0.1140117421746254, 0.11409436911344528, 0.14921021461486816, 0.14504361152648926, 0.15939901769161224, 0.1779724508523941, 0.2093481570482254, 0.18844424188137054, 0.13224180042743683, 0.16347694396972656, 0.14944233000278473, 0.17428486049175262, 0.17120762169361115, 0.1694408506155014, 0.19549405574798584, 0.16715717315673828, 0.20076380670070648, 0.09246378391981125, 0.16012343764305115, 0.11676663905382156, 0.16207832098007202, 0.11172108352184296, 0.14037270843982697, 0.14478830993175507, 0.17409372329711914, 0.11405035108327866, 0.17207440733909607, 0.14758996665477753, 0.15541398525238037, 0.113568015396595, 0.14228790998458862, 0.1516968309879303, 0.09200859069824219, 0.17329899966716766, 0.10413306951522827, 0.1444982886314392, 0.16456978023052216, 0.18034255504608154, 0.09287967532873154, 0.11207856237888336, 0.14479060471057892, 0.13383924961090088, 0.1582888811826706, 0.1170881986618042, 0.1421307474374771, 0.14925117790699005, 0.14727818965911865, 0.1477106511592865, 0.19059477746486664, 0.15269671380519867, 0.19703423976898193, 0.1571187973022461, 0.16389955580234528, 0.13530392944812775, 0.15727025270462036, 0.1482255458831787, 0.11289740353822708, 0.15245267748832703, 0.12888334691524506, 0.15328292548656464, 0.1524626761674881, 0.1839653104543686, 0.1690838783979416, 0.15326617658138275, 0.1772747039794922, 0.16028182208538055, 0.18908654153347015, 0.15633252263069153, 0.19574344158172607, 0.28710776567459106, 0.08080289512872696, 0.19649295508861542, 0.1770792007446289, 0.15933993458747864, 0.16196903586387634, 0.11436599493026733, 0.1681521236896515, 0.11157084256410599, 0.15889328718185425, 0.16910310089588165, 0.18154583871364594, 0.10448630154132843, 0.1536037027835846, 0.09866193681955338, 0.14782582223415375, 0.10608694702386856, 0.16146288812160492, 0.11417697370052338, 0.18275174498558044, 0.18473075330257416, 0.1703193634748459, 0.15737754106521606, 0.21351943910121918, 0.16878387331962585, 0.1878972202539444, 0.12559932470321655, 0.1410793513059616, 0.11867484450340271, 0.13018712401390076, 0.18110568821430206, 0.1622420847415924, 0.12830260396003723, 0.18005217611789703, 0.8700586557388306, 1.3369859457015991, 0.8054104447364807, 1.4911766052246094, 0.7830772399902344, 1.1578850746154785, 1.0308641195297241, 1.3370840549468994, 1.0321414470672607, 1.0665048360824585, 0.6743813753128052, 1.6025032997131348, 1.1946568489074707, 1.1285419464111328, 1.1109893321990967, 0.986017644405365, 1.593517541885376, 0.9851148724555969, 1.2525238990783691, 1.3947639465332031, 1.0615360736846924, 1.267461895942688, 1.3081480264663696, 1.8377325534820557, 1.4158445596694946, 1.7513079643249512, 0.9387469291687012, 1.0254371166229248, 1.8980422019958496, 1.94662344455719, 0.9657720923423767, 1.5134073495864868, 0.9997892379760742, 1.261322021484375, 1.00886070728302, 0.8569464683532715, 1.564353585243225, 1.2077038288116455, 0.9107874035835266, 1.2318543195724487, 2.019423723220825, 1.7661099433898926, 1.3513914346694946, 1.362725853919983, 2.3073058128356934, 0.9440057873725891, 1.0986056327819824, 1.5174223184585571, 2.0124905109405518, 0.844654381275177, 1.0216904878616333, 1.2985286712646484, 1.2899755239486694, 1.4781675338745117, 0.8699830174446106, 2.330502510070801, 1.4797124862670898, 1.1335837841033936, 1.6244242191314697, 0.9499414563179016, 0.95474773645401, 1.3354500532150269, 0.8192483186721802, 1.395064353942871, 1.6525096893310547, 1.4819942712783813, 1.3667376041412354, 1.2308690547943115, 1.7713898420333862, 0.8795032501220703, 1.1851577758789062, 1.565523624420166, 0.947100818157196, 1.181535005569458, 1.2290172576904297, 1.5701760053634644, 1.3673412799835205, 1.5270205736160278, 0.9499266743659973, 1.413533329963684, 0.798643171787262, 0.6545445322990417, 1.3499195575714111, 0.8992055058479309, 1.2171450853347778, 1.5223493576049805, 1.0889949798583984, 1.5038201808929443, 0.9980154037475586, 1.4229313135147095, 0.5461164712905884, 1.1795438528060913, 0.8214877247810364, 0.7391825914382935, 1.1314183473587036, 1.3065308332443237, 1.143789291381836, 1.5096355676651, 1.486840844154358, 1.081761121749878, 1.3343476057052612, 1.6153185367584229, 0.855516791343689, 0.7553534507751465, 0.6771978139877319, 1.6888993978500366, 0.8922767639160156, 1.7847589254379272, 1.4219814538955688, 1.305432677268982, 1.0340696573257446, 0.6426199078559875, 0.8489233255386353, 1.4892038106918335, 1.9241949319839478, 2.0332586765289307, 0.8221356272697449, 1.758950114250183, 2.0299928188323975, 1.5259313583374023, 1.032110333442688, 0.9353341460227966, 0.7364854216575623, 1.9235906600952148, 0.9410683512687683, 1.3721342086791992, 1.567956566810608, 1.3572251796722412, 1.2387926578521729, 1.793030023574829, 2.061387538909912, 0.9851039052009583, 1.0729084014892578, 1.3879950046539307, 1.3630329370498657, 0.9389913082122803, 0.8601423501968384, 0.7971464395523071, 0.8924376964569092, 1.329148530960083, 1.570520043373108, 1.1484227180480957, 0.7123697996139526, 1.027299404144287, 1.246053695678711, 1.1897860765457153, 1.020248532295227, 1.0271353721618652, 1.53090238571167, 0.9679409861564636, 0.5753239989280701, 1.2325804233551025, 0.6568886637687683, 0.8771365284919739, 0.9665618538856506, 1.0261738300323486, 0.5305548310279846, 1.569688081741333, 1.2123807668685913, 0.5766831040382385, 1.4474503993988037, 1.423445224761963, 0.8135563731193542, 1.323954701423645, 1.35496985912323, 1.5433870553970337, 1.0965838432312012, 0.8117313385009766, 1.0668554306030273, 0.6923995018005371, 1.204111933708191, 0.9880797863006592, 1.218955159187317, 0.7564945220947266, 1.05810546875, 1.2642993927001953, 1.6229891777038574, 1.0489811897277832, 0.927821934223175, 1.4999512434005737, 1.5073107481002808, 1.2878167629241943, 1.0451297760009766, 1.3185818195343018, 0.8279711008071899, 0.6321976184844971, 0.6843568086624146, 0.9090253114700317, 1.2185145616531372, 1.7034735679626465, 0.9234382510185242, 0.9044626355171204, 0.9438958764076233, 1.1231303215026855, 1.2594430446624756, 1.0418872833251953, 0.998289942741394, 1.3625649213790894, 1.0592344999313354, 1.0640745162963867, 1.1881544589996338, 2.195197343826294, 1.3243257999420166, 1.2947663068771362, 0.6466887593269348, 1.913630485534668, 0.7792993187904358, 1.588135004043579, 1.0351653099060059, 1.0300532579421997, 1.1175740957260132, 0.7864550352096558, 0.875079333782196, 1.670396327972412, 0.8041827082633972, 1.5260626077651978, 1.2309218645095825, 0.9325241446495056, 1.0204538106918335, 1.1143516302108765, 1.326757788658142, 1.3748213052749634, 1.8076635599136353, 1.0732591152191162, 1.3691338300704956, 1.2201097011566162, 1.5598986148834229, 0.796455979347229, 1.1623258590698242, 2.124563455581665, 1.2485356330871582, 1.1089849472045898, 0.9230554103851318, 1.1519818305969238, 1.50775146484375, 1.6518163681030273, 0.9042739868164062, 1.0882936716079712, 1.1571812629699707, 0.7610756754875183, 1.2438833713531494, 1.4942760467529297, 0.7977040410041809, 1.0895042419433594, 0.996697187423706, 0.8256651163101196, 0.7135282754898071, 1.1059271097183228, 1.3098623752593994, 1.7601220607757568, 1.9384454488754272, 1.5177967548370361, 1.299540638923645, 1.9559115171432495, 1.4850687980651855, 1.3440109491348267, 1.1357167959213257, 1.2726385593414307, 1.1606979370117188, 0.9537972807884216, 1.6340818405151367, 1.438020944595337, 1.3362541198730469, 0.9199143648147583, 0.8030825853347778, 1.3899952173233032, 1.293221354484558, 1.325408935546875, 0.8024987578392029, 0.8723016977310181, 1.4048922061920166, 1.51296865940094, 1.0562975406646729, 1.1547387838363647, 1.042708158493042, 1.5030605792999268, 0.9672643542289734, 1.0970149040222168, 0.8165374398231506, 1.0674424171447754, 0.7552123069763184, 1.0037741661071777, 0.7178219556808472, 0.7776355743408203, 1.2026710510253906, 0.7422353029251099, 1.542676568031311, 0.9092900156974792, 1.5603708028793335, 2.1521999835968018, 2.0927469730377197, 1.2831170558929443, 1.7648617029190063, 0.6220468282699585, 1.3793613910675049, 0.8005034923553467, 1.3801134824752808, 1.159924864768982, 0.9738785624504089, 1.886664867401123, 105.93778228759766, 255.6942901611328, 141.97889709472656, 16.389408111572266, 62.29836654663086, 73.77180480957031, 63.490478515625, 259.3310546875, 33.14984130859375, 139.91909790039062, 117.07994079589844, 188.00030517578125, 77.75373077392578, 158.4105682373047, 44.345550537109375, 330.27069091796875, 158.3866424560547, 32.235572814941406, 49.031951904296875, 53.73781967163086, 195.74644470214844, 53.47532272338867, 118.8519287109375, 78.8791275024414, 115.37833404541016, 118.64276885986328, 137.90789794921875, 67.18716430664062, 107.85070037841797, 23.81828498840332, 144.44476318359375, 92.21585845947266, 67.78079223632812, 57.238563537597656, 68.91325378417969, 38.86004638671875, 77.77919006347656, 144.47518920898438, 162.31314086914062, 44.11013412475586, 106.5072021484375, 44.7672119140625, 64.08425903320312, 22.97392463684082, 39.74748992919922, 134.12611389160156, 17.28167724609375, 85.92446899414062, 142.70669555664062, 118.8653564453125, 80.28750610351562, 217.35467529296875, 36.428680419921875, 155.66693115234375, 39.541748046875, 88.10711669921875, 52.591064453125, 86.58172607421875, 62.71435546875, 56.071014404296875, 72.51323699951172, 77.21038818359375, 102.16435241699219, 79.846435546875, 50.78458786010742, 182.17413330078125, 141.95880126953125, 135.30738830566406, 153.3504638671875, 218.80101013183594, 114.53108978271484, 59.03683853149414, 22.863494873046875, 303.0516052246094, 54.38630676269531, 29.10333251953125, 104.26329803466797, 147.17926025390625, 31.335712432861328, 244.1763458251953, 29.59771728515625, 145.53038024902344, 58.524017333984375, 82.1930923461914, 52.221893310546875, 141.65185546875, 188.9234161376953, 92.5440444946289, 28.5235595703125, 83.46250915527344, 44.469451904296875, 223.71926879882812, 156.52523803710938, 171.3724365234375, 50.88616943359375, 77.19536590576172, 87.45466613769531, 81.65694427490234, 64.249267578125, 101.39238739013672, 85.77784729003906, 34.67121124267578, 60.84829330444336, 112.16851043701172, 82.4981460571289, 22.708261489868164, 76.64032745361328, 22.028959274291992, 159.1146240234375, 147.5150146484375, 130.27963256835938, 310.98834228515625, 21.14666748046875, 48.363826751708984, 54.57220458984375, 88.7491226196289, 23.472412109375, 77.44609069824219, 75.15231323242188, 147.296142578125, 170.71253967285156, 112.41851043701172, 36.80582046508789, 96.5363540649414, 36.4508056640625, 42.09122848510742, 19.43231201171875, 58.52681350708008, 116.6261215209961, 140.42156982421875, 97.79388427734375, 20.999374389648438, 182.63552856445312, 43.82754135131836, 100.66193389892578, 120.48609924316406, 154.9906005859375, 69.31045532226562, 94.9603271484375, 117.536865234375, 64.9173583984375, 72.56644439697266, 27.3267822265625, 91.29146575927734, 28.59552001953125, 177.7859344482422, 96.31352996826172, 44.15278244018555, 53.35878372192383, 121.19940948486328, 52.025390625, 34.40946960449219, 29.9488525390625, 88.19845581054688, 24.90949821472168, 70.86310577392578, 54.4173583984375, 69.53559875488281, 21.37982177734375, 40.07695388793945, 100.67423248291016, 117.0906982421875, 101.7012710571289, 142.53314208984375, 220.95965576171875, 66.39273071289062, 110.9969482421875, 193.5161895751953, 94.18971252441406, 51.214412689208984, 138.6160888671875, 29.7025146484375, 33.71546173095703, 33.01708984375, 118.28185272216797, 27.42242431640625, 87.23699951171875, 26.462493896484375, 51.85546875, 27.160736083984375, 26.4488525390625, 53.74955749511719, 114.98149871826172, 30.492677688598633, 20.813884735107422, 189.69683837890625, 42.90087890625, 22.240175247192383, 90.04695129394531, 127.84466552734375, 42.846946716308594, 202.2824249267578, 176.617919921875, 26.17474365234375, 77.5254135131836, 31.767290115356445, 137.9464874267578, 254.6454620361328, 40.3981819152832, 30.99678611755371, 85.2485122680664, 31.17436981201172, 28.96636962890625, 150.61968994140625, 75.9254150390625, 107.77690887451172, 124.86502838134766, 95.7684097290039, 97.77982330322266, 155.95318603515625, 184.3909912109375, 55.44277572631836, 53.957820892333984, 105.7763442993164, 81.05719757080078, 38.0166015625, 24.06268310546875, 67.19243621826172, 31.847440719604492, 83.8467788696289, 43.28558349609375, 33.11927032470703, 135.5418701171875, 333.28375244140625, 140.39422607421875, 41.6767578125, 111.77218627929688, 55.65351867675781, 27.50434684753418, 37.48630905151367, 20.881410598754883, 34.6768798828125, 45.539764404296875, 101.871826171875, 159.04307556152344, 107.5375747680664, 153.19073486328125, 58.97540283203125, 155.30471801757812, 65.0926513671875, 112.04473114013672, 27.62506103515625, 110.32241821289062, 166.55044555664062, 118.67472076416016, 41.472713470458984, 101.46822357177734, 79.60342407226562, 85.5960693359375, 132.87164306640625, 103.16703033447266, 108.9461669921875, 129.5438690185547, 86.24771118164062, 27.659515380859375, 49.2227668762207, 74.12222290039062, 98.6049575805664, 119.9259262084961, 30.539154052734375, 46.17007827758789, 88.2603530883789, 225.9368896484375, 108.5121078491211, 111.9388656616211, 141.1165771484375, 39.065242767333984, 86.80107879638672, 186.96975708007812, 84.04488372802734, 92.47425842285156, 161.36749267578125, 182.2738037109375, 120.42356872558594, 52.29248046875, 37.60615921020508, 46.559783935546875, 75.67076110839844, 51.643310546875, 47.79427719116211, 49.89723587036133, 96.045166015625, 131.0594940185547, 100.55333709716797, 67.79007720947266, 87.53543090820312, 28.121044158935547, 30.05693817138672, 82.68374633789062, 32.96352767944336, 40.3908576965332, 38.1201171875, 28.384376525878906, 131.3250732421875, 26.253910064697266, 78.76237487792969, 120.68099212646484, 32.38486099243164, 119.80615234375, 120.49878692626953, 3.409639835357666, 1.970475435256958, 1.1641759872436523, 2.2328405380249023, 2.128066062927246, 2.91995906829834, 2.817833185195923, 1.679546594619751, 1.9403562545776367, 2.6914424896240234, 3.054872751235962, 2.276069402694702, 3.216031312942505, 2.268542528152466, 2.364171028137207, 1.5760374069213867, 1.5369207859039307, 2.0497169494628906, 2.272425413131714, 3.079871416091919, 1.8306429386138916, 2.4357850551605225, 2.096010684967041, 2.7387547492980957, 1.6771670579910278, 2.13498592376709, 2.8007004261016846, 3.053778886795044, 2.635314464569092, 1.8993620872497559, 1.7108891010284424, 2.8865275382995605, 3.801319122314453, 2.273674964904785, 2.396183967590332, 3.953200578689575, 2.0409185886383057, 3.0754382610321045, 2.374321937561035, 2.0934019088745117, 2.2416741847991943, 1.3728969097137451, 1.4288915395736694, 2.6811041831970215, 2.5756545066833496, 2.517695903778076, 3.115530252456665, 3.6283538341522217, 1.9609928131103516, 1.796975016593933, 2.8497607707977295, 2.1527621746063232, 2.822068929672241, 1.4605958461761475, 2.8000500202178955, 3.0078606605529785, 3.4671642780303955, 2.737605333328247, 2.823880434036255, 2.9204554557800293, 2.3682851791381836, 2.2862582206726074, 3.153559446334839, 3.5457255840301514, 1.4836111068725586, 2.2595365047454834, 1.5154576301574707, 1.646270751953125, 2.4705381393432617, 2.464172124862671, 2.3413264751434326, 1.5679978132247925, 2.98551082611084, 3.614140033721924, 2.3615200519561768, 2.931079864501953, 1.7147339582443237, 1.8061470985412598, 3.0820629596710205, 1.614388346672058, 2.4067976474761963, 2.3940517902374268, 3.118147611618042, 1.8346312046051025, 1.5792620182037354, 2.9234209060668945, 2.9752557277679443, 1.6173337697982788, 3.1567773818969727, 1.3322802782058716, 2.5679681301116943, 2.650686025619507, 2.1746950149536133, 2.2785093784332275, 2.862889289855957, 1.4858274459838867, 2.4343440532684326, 2.8335323333740234, 2.5641491413116455, 1.8156920671463013, 2.0015575885772705, 1.3313959836959839, 2.4443178176879883, 1.4457062482833862, 1.9700384140014648, 2.689565420150757, 2.5367860794067383, 1.7515478134155273, 3.739811897277832, 2.0914721488952637, 2.2567970752716064, 2.493161678314209, 2.2226743698120117, 2.3738527297973633, 2.9753475189208984, 1.2717543840408325, 2.836664915084839, 3.562337875366211, 2.850282907485962, 2.8035545349121094, 2.62896728515625, 1.63461172580719, 2.3022944927215576, 2.9022133350372314, 2.4711966514587402, 3.0923867225646973, 2.7636168003082275, 3.2777280807495117, 2.780576705932617, 2.0428247451782227, 3.201216459274292, 2.6442465782165527, 2.772883892059326, 1.9942697286605835, 2.4598283767700195, 2.422189474105835, 2.789508104324341, 2.6870031356811523, 1.2166165113449097, 1.5952385663986206, 1.7414987087249756, 1.8851555585861206, 2.1411027908325195, 2.8560736179351807, 2.2179946899414062, 1.8154648542404175, 2.8631014823913574, 2.3747334480285645, 1.59139084815979, 1.7502241134643555, 3.1600029468536377, 2.6866142749786377, 2.561751127243042, 2.5797510147094727, 2.475320816040039, 2.8696179389953613, 1.941811442375183, 2.286391496658325, 3.704056978225708, 2.092226982116699, 2.0934407711029053, 3.4488537311553955, 1.574999213218689, 3.366774320602417, 2.733283519744873, 2.729022264480591, 1.869384527206421, 2.068718910217285, 2.6326653957366943, 3.391017436981201, 2.141646385192871, 1.4638433456420898, 1.8584089279174805, 1.7505542039871216, 2.239597797393799, 1.5951659679412842, 3.7056760787963867, 2.0421135425567627, 2.5644216537475586, 2.605689287185669, 2.8571243286132812, 2.098165512084961, 3.1920013427734375, 2.683091402053833, 3.1218767166137695, 1.8706556558609009, 3.429936170578003, 3.1183862686157227, 1.537398338317871, 3.387144088745117, 2.0308306217193604, 3.886608839035034, 1.830633521080017, 2.059988021850586, 2.2495570182800293, 2.4137370586395264, 3.2162411212921143, 2.7456483840942383, 2.1162519454956055, 1.8466020822525024, 1.4698494672775269, 3.3690805435180664, 1.7278285026550293, 1.7381638288497925, 2.8168017864227295, 2.730057954788208, 1.9908517599105835, 2.204678535461426, 2.5573172569274902, 2.4555630683898926, 3.5501015186309814, 2.9361987113952637, 2.3714003562927246, 2.7023820877075195, 3.3263652324676514, 2.2736458778381348, 3.545154571533203, 2.027865409851074, 2.6317431926727295, 1.8119524717330933, 2.2550406455993652, 2.5415990352630615, 2.175758123397827, 3.2766637802124023, 2.3665030002593994, 1.2320185899734497, 1.807070016860962, 3.057018756866455, 2.7524807453155518, 2.4691286087036133, 2.504331588745117, 3.5791015625, 3.5950536727905273, 2.0944578647613525, 2.346524238586426, 2.556342363357544, 1.6745376586914062, 1.999951720237732, 3.8611550331115723, 2.395676851272583, 1.42239248752594, 3.2205235958099365, 2.1813724040985107, 2.9859514236450195, 1.573926329612732, 3.114433765411377, 2.6811766624450684, 3.1077072620391846, 1.9613218307495117, 2.391780138015747, 2.8178319931030273, 2.558500289916992, 2.772472381591797, 1.8125208616256714, 3.4691576957702637, 2.3237662315368652, 2.2205514907836914, 2.340327739715576, 2.43634295463562, 1.7702610492706299, 1.5751720666885376, 2.6845703125, 2.3570451736450195, 2.5537784099578857, 2.369563579559326, 2.6400115489959717, 3.056281089782715, 3.286168098449707, 2.663869619369507, 3.0257720947265625, 3.788769483566284, 1.546492576599121, 2.9380035400390625, 1.6964941024780273, 2.5151987075805664, 3.0394933223724365, 2.0347490310668945, 2.912450075149536, 2.276235342025757, 2.138779878616333, 2.104058265686035, 3.070751190185547, 2.05539608001709, 2.5939290523529053, 2.5481812953948975, 1.9007024765014648, 1.9531909227371216, 1.36443030834198, 1.398211121559143, 2.6430559158325195, 2.0605764389038086, 3.249911308288574, 3.434075355529785, 2.4255266189575195, 2.0839109420776367, 2.7287819385528564, 3.5414304733276367, 1.897292137145996, 1.6995861530303955, 1.5477089881896973, 0.08020945638418198, 0.17058265209197998, 0.1525442898273468, 0.18919768929481506, 0.16127164661884308, 0.15814201533794403, 0.11633527278900146, 0.16428862512111664, 0.18320544064044952, 0.1577008217573166, 0.18666307628154755, 0.15929631888866425, 0.1932828426361084, 0.13939768075942993, 0.09779056161642075, 0.18622027337551117, 0.1718660444021225, 0.14079324901103973, 0.08009237051010132, 0.14617861807346344, 0.16499625146389008, 0.2326163500547409, 0.16877834498882294, 0.19430950284004211, 0.1694723516702652, 0.10546044260263443, 0.170053169131279, 0.15497560799121857, 0.114441879093647, 0.19015458226203918, 0.1569335162639618, 0.1587650328874588, 0.17068007588386536, 0.1541319042444229, 0.15938153862953186, 0.13959096372127533, 0.2156856805086136, 0.14369891583919525, 0.1626208871603012, 0.19535896182060242, 0.2141566276550293, 0.09047655016183853, 0.13552187383174896, 0.14979511499404907, 0.14886456727981567, 0.08854368329048157, 0.10848817229270935, 0.07921525090932846, 0.17741386592388153, 0.19642886519432068, 0.16272518038749695, 0.1149023100733757, 0.11997298896312714, 0.13138766586780548, 0.12326511740684509, 0.1385757327079773, 0.1393844187259674, 0.1613467037677765, 0.1725698858499527, 0.16724446415901184, 0.20979541540145874, 0.12492293119430542, 0.13692355155944824, 0.20821841061115265, 0.16952811181545258, 0.19057199358940125, 0.18822216987609863, 0.15816567838191986, 0.18169963359832764, 0.14093804359436035, 0.13321749866008759, 0.0641380324959755, 0.1348486840724945, 0.2175581306219101, 0.11787106841802597, 0.21126975119113922, 0.11918999999761581, 0.18814688920974731, 0.1354699730873108, 0.13242244720458984, 0.14679734408855438, 0.20303495228290558, 0.16117535531520844, 0.133542001247406, 0.21305137872695923, 0.10626258701086044, 0.1214979737997055, 0.11041990667581558, 0.15078949928283691, 0.07461723685264587, 0.20808230340480804, 0.17035619914531708, 0.1433783769607544, 0.1318831592798233, 0.21900716423988342, 0.11498258262872696, 0.1224362850189209, 0.19874893128871918, 0.17293967306613922, 0.16864395141601562, 0.16545139253139496, 0.16570864617824554, 0.1590936928987503, 0.13706332445144653, 0.1702466756105423, 0.14854460954666138, 0.15363092720508575, 0.13985194265842438, 0.11878503859043121, 0.11668151617050171, 0.10223104059696198, 0.16908161342144012, 0.1865072250366211, 0.1305283010005951, 0.17250266671180725, 0.07388029992580414, 0.205708846449852, 0.17468863725662231, 0.19958515465259552, 0.17081981897354126, 0.16964758932590485, 0.1526690423488617, 0.19261980056762695, 0.12728045880794525, 0.1775132268667221, 0.1681404858827591, 0.15168893337249756, 0.1436426341533661, 0.17873899638652802, 0.11371824145317078, 0.14243125915527344, 0.14210043847560883, 0.1308603584766388, 0.21819782257080078, 0.16635914146900177, 0.22273415327072144, 0.2130848616361618, 0.1247389167547226, 0.1603250503540039, 0.14215625822544098, 0.16315674781799316, 0.15423312783241272, 0.1614353507757187, 0.16112422943115234, 0.1710256189107895, 0.1259956806898117, 0.18891099095344543, 0.17043909430503845, 0.21458972990512848, 0.25752151012420654, 0.16873151063919067, 0.08931449800729752, 0.13424429297447205, 0.17525726556777954, 0.1219099760055542, 0.08037740737199783, 0.15131719410419464, 0.09622500091791153, 0.1172415167093277, 0.1573064923286438, 0.1902456283569336, 0.20256257057189941, 0.167087584733963, 0.11136879026889801, 0.14179199934005737, 0.11951208859682083, 0.14342567324638367, 0.15720832347869873, 0.15892095863819122, 0.17895565927028656, 0.12727470695972443, 0.1324455738067627, 0.15728802978992462, 0.1134161427617073, 0.1690571904182434, 0.1340288370847702, 0.07953841239213943, 0.21526336669921875, 0.13698072731494904, 0.11254850029945374, 0.19163306057453156, 0.1768106371164322, 0.13112984597682953, 0.17753159999847412, 0.1457979679107666, 0.18062366545200348, 0.19304630160331726, 0.14904968440532684, 0.2050999402999878, 0.18422961235046387, 0.18889077007770538, 0.17469936609268188, 0.17210334539413452, 0.1344108283519745, 0.1847839653491974, 0.18420875072479248, 0.1821412593126297, 0.11468622833490372, 0.1608535349369049, 0.13885736465454102, 0.13002046942710876, 0.16401299834251404, 0.1868886947631836, 0.15495580434799194, 0.14596420526504517, 0.14650067687034607, 0.15898209810256958, 0.16950933635234833, 0.17131268978118896, 0.18809516727924347, 0.1980264037847519, 0.2016318440437317, 0.09940554201602936, 0.1793285310268402, 0.14676907658576965, 0.1750679612159729, 0.11725500971078873, 0.17009036242961884, 0.1490509808063507, 0.19403880834579468, 0.0958598330616951, 0.09620896726846695, 0.15127262473106384, 0.13371944427490234, 0.05176388472318649, 0.1629553884267807, 0.12468305975198746, 0.1499728113412857, 0.15278974175453186, 0.21155677735805511, 0.22236035764217377, 0.1433989703655243, 0.18511278927326202, 0.10236722975969315, 0.16033342480659485, 0.20601065456867218, 0.21787673234939575, 0.1477356106042862, 0.15088419616222382, 0.17105033993721008, 0.15927229821681976, 0.15132446587085724, 0.197539821267128, 0.16133657097816467, 0.08534398674964905, 0.17056883871555328, 0.10284527391195297, 0.13102710247039795, 0.15081565082073212, 0.11987550556659698, 0.1320132613182068, 0.15571270883083344, 0.15872643887996674, 0.14610710740089417, 0.15986430644989014, 0.16066136956214905, 0.11492490768432617, 0.20716363191604614, 0.1862572878599167, 0.0706746056675911, 0.14419174194335938, 0.2224174290895462, 0.25495457649230957, 0.2640713155269623, 0.1662817746400833, 0.15320563316345215, 0.1319727897644043, 0.1790364384651184, 0.14243561029434204, 0.16984884440898895, 0.1099153459072113, 0.06296742707490921, 0.14864671230316162, 0.19769763946533203, 0.18741253018379211, 0.1404104232788086, 0.17342710494995117, 0.18087157607078552, 0.0874599814414978, 0.08949519693851471, 0.17527534067630768, 0.12608851492404938, 0.1353473663330078, 0.12009637802839279, 0.09490949660539627, 0.2311478555202484, 0.09683060646057129, 0.1641744077205658, 0.16949020326137543, 0.13221803307533264, 0.09109500795602798, 0.13470256328582764, 0.17272642254829407, 0.14907938241958618, 0.2065432369709015, 0.09046125411987305, 0.13246378302574158, 0.20553386211395264, 0.16263236105442047, 0.1008315235376358, 1.428053855895996, 0.9728673100471497, 0.795231282711029, 1.4400601387023926, 0.944469153881073, 1.050499439239502, 1.7433831691741943, 0.8055610656738281, 0.8832061290740967, 1.0656548738479614, 1.7274466753005981, 1.561302900314331, 1.5187937021255493, 1.6512846946716309, 1.91298508644104, 1.656014084815979, 1.6669384241104126, 1.2300570011138916, 2.029460906982422, 1.329591989517212, 1.5304673910140991, 1.4335435628890991, 1.4099334478378296, 0.9331777691841125, 1.4412081241607666, 1.432940125465393, 0.7834814190864563, 1.4782530069351196, 1.7518644332885742, 1.513744592666626, 1.3936214447021484, 1.7737350463867188, 1.0514132976531982, 1.0837292671203613, 1.3436925411224365, 2.1815297603607178, 0.8356429934501648, 1.5697847604751587, 1.5903643369674683, 1.853806972503662, 1.4610470533370972, 1.7247320413589478, 2.399639844894409, 1.5786463022232056, 1.0099149942398071, 0.8794640898704529, 1.578713297843933, 1.1320443153381348, 0.7805495262145996, 0.920098066329956, 2.2833328247070312, 1.9403736591339111, 1.602868914604187, 1.0106761455535889, 1.6367424726486206, 0.9441148042678833, 1.167766809463501, 1.0247749090194702, 1.3397878408432007, 1.7844622135162354, 1.0332638025283813, 1.3045971393585205, 1.5582259893417358, 1.3254655599594116, 0.8194918632507324, 1.2204911708831787, 1.286908507347107, 1.253908634185791, 0.9672152996063232, 2.0737314224243164, 1.29766047000885, 1.2308125495910645, 0.6815922260284424, 0.9443576335906982, 1.6490049362182617, 1.434523582458496, 1.2499432563781738, 1.1312823295593262, 0.9294482469558716, 0.6952090263366699, 0.9644178748130798, 1.4625338315963745, 0.9092541933059692, 1.6661949157714844, 1.081529140472412, 0.7166088819503784, 0.963988184928894, 1.489083170890808, 1.0058823823928833, 0.9053654074668884, 0.8314315676689148, 1.666689395904541, 1.4174085855484009, 1.7039762735366821, 0.8834357261657715, 0.9603411555290222, 1.7869186401367188, 1.0559849739074707, 1.0713884830474854, 2.1209700107574463, 1.4083433151245117, 0.8725156784057617, 1.0550956726074219, 1.4502155780792236, 1.1780033111572266, 1.1605243682861328, 1.1873241662979126, 1.098354458808899, 1.0738978385925293, 1.737012267112732, 1.8465631008148193, 1.3958001136779785, 1.4618685245513916, 1.1035128831863403, 0.39816465973854065, 1.4116357564926147, 0.7055964469909668, 1.370797038078308, 0.9638445973396301, 1.515360951423645, 0.775555431842804, 0.863184928894043, 1.2134208679199219, 1.3733325004577637, 1.10784113407135, 0.8367630839347839, 1.1714808940887451, 0.7870964407920837, 0.9286891222000122, 1.064616084098816, 1.4453719854354858, 1.4357980489730835, 1.0774950981140137, 1.3578354120254517, 1.6436747312545776, 1.996540904045105, 1.3343998193740845, 1.150834321975708, 1.6523488759994507, 1.0428848266601562, 1.5298649072647095, 0.9325936436653137, 1.5629912614822388, 1.3369718790054321, 1.5440691709518433, 0.9169148206710815, 1.0930712223052979, 0.8904998302459717, 0.6938989758491516, 1.3608524799346924, 0.8757349848747253, 1.1072956323623657, 1.3422040939331055, 0.6366369724273682, 1.649981141090393, 1.4147752523422241, 0.8611955046653748, 1.6515716314315796, 0.7013293504714966, 1.6862308979034424, 1.4738174676895142, 1.045093059539795, 1.2093075513839722, 1.139605164527893, 1.0532282590866089, 1.1221648454666138, 0.9475552439689636, 1.0275588035583496, 1.0907713174819946, 1.1625149250030518, 0.8977978229522705, 0.7345290780067444, 1.075430154800415, 0.9041279554367065, 0.9150741100311279, 1.012128472328186, 1.051020622253418, 0.982326865196228, 0.7963050603866577, 1.2990304231643677, 1.246812343597412, 1.3093940019607544, 0.6788186430931091, 1.138924479484558, 1.7672103643417358, 1.6189556121826172, 1.2654697895050049, 1.1887131929397583, 0.7082282900810242, 1.2188104391098022, 0.854664146900177, 1.3624136447906494, 0.3612581789493561, 0.8920556306838989, 1.0394091606140137, 1.2862519025802612, 1.069185495376587, 0.8953387141227722, 1.5991395711898804, 1.3904072046279907, 0.6931705474853516, 1.494508981704712, 0.7927326560020447, 0.8600132465362549, 0.9966530203819275, 0.8171831369400024, 1.3446191549301147, 1.5021722316741943, 1.0726066827774048, 1.713415503501892, 1.0822559595108032, 1.4004305601119995, 0.8895357251167297, 1.507027506828308, 1.2477116584777832, 0.9810401797294617, 1.1366366147994995, 1.1853231191635132, 0.9490128755569458, 1.0619239807128906, 1.4242881536483765, 0.9076024293899536, 1.9011259078979492, 2.016503095626831, 1.3374743461608887, 1.4374799728393555, 1.0792760848999023, 0.9963790774345398, 1.2255736589431763, 1.475740909576416, 1.7646844387054443, 1.6057974100112915, 1.2383942604064941, 0.7324565052986145, 1.5201410055160522, 1.490411639213562, 0.8324030041694641, 0.794903576374054, 1.218977451324463, 2.9081859588623047, 1.0848908424377441, 1.227225422859192, 1.0654380321502686, 1.637101411819458, 1.0475187301635742, 1.6133337020874023, 1.4760485887527466, 0.5025948882102966, 0.9944554567337036, 2.6188714504241943, 1.0774410963058472, 1.423137903213501, 1.4165704250335693, 1.9817653894424438, 1.3459442853927612, 1.6583683490753174, 1.3057138919830322, 1.0009316205978394, 1.3949648141860962, 1.4184731245040894, 1.118227481842041, 0.8754223585128784, 1.234284520149231, 1.6845192909240723, 1.1065880060195923, 1.2912805080413818, 1.1124093532562256, 0.7997541427612305, 0.8870213627815247, 1.0933799743652344, 1.1561589241027832, 1.7365877628326416, 0.8941311240196228, 1.0720995664596558, 1.0538091659545898, 1.4977624416351318, 1.5691626071929932, 0.9664550423622131, 1.6382830142974854, 0.49003854393959045, 1.4865375757217407, 0.9023253917694092, 1.2200156450271606, 1.575701355934143, 1.699388027191162, 0.782659113407135, 1.5268404483795166, 1.6732511520385742, 1.5376485586166382, 1.0789470672607422, 1.9933000802993774, 1.7664705514907837, 1.9227510690689087, 1.2224657535552979, 1.0650460720062256, 1.6668542623519897, 0.8936700224876404, 0.7285980582237244, 1.5387823581695557, 1.9013149738311768, 180.1013946533203, 96.3631820678711, 212.91128540039062, 55.857791900634766, 25.13690185546875, 151.65093994140625, 131.6074981689453, 72.7935791015625, 108.93294525146484, 50.00339889526367, 92.77734375, 20.6776123046875, 123.07513427734375, 73.5008544921875, 51.41400909423828, 152.73548889160156, 27.076995849609375, 30.30555534362793, 49.95583724975586, 31.516605377197266, 87.9163818359375, 126.96136474609375, 124.93782806396484, 34.4234619140625, 248.3502655029297, 33.931884765625, 80.59233856201172, 44.84188461303711, 24.8914794921875, 138.97344970703125, 106.03722381591797, 168.14144897460938, 78.19769287109375, 110.33837890625, 120.45503997802734, 43.67108154296875, 66.09294128417969, 106.78689575195312, 63.67068099975586, 100.7133560180664, 134.2296905517578, 17.678070068359375, 102.087158203125, 115.28475952148438, 107.2626953125, 195.02110290527344, 29.06201171875, 34.64956283569336, 38.494937896728516, 33.54547119140625, 36.56353759765625, 64.5718994140625, 126.4404296875, 149.7503662109375, 138.4783477783203, 112.51953125, 52.18949890136719, 69.47177124023438, 101.49614715576172, 46.515472412109375, 33.81298828125, 25.11929702758789, 113.89877319335938, 140.4988250732422, 136.80575561523438, 22.99609375, 114.88750457763672, 77.79033660888672, 60.50482177734375, 147.636962890625, 99.53813934326172, 76.90736389160156, 39.26934814453125, 56.15496826171875, 122.20561981201172, 141.26263427734375, 141.93902587890625, 44.820037841796875, 86.58638763427734, 37.11253356933594, 128.0693359375, 137.204833984375, 151.3043670654297, 73.21636199951172, 104.60445404052734, 47.80316162109375, 57.50026321411133, 30.65751075744629, 84.72003936767578, 43.58984375, 63.26594543457031, 216.69549560546875, 66.24185180664062, 43.71009826660156, 17.741016387939453, 49.70934295654297, 96.05892181396484, 123.68706512451172, 66.03397369384766, 72.42788696289062, 99.12236785888672, 125.83894348144531, 157.2218475341797, 61.28184509277344, 44.82180404663086, 23.142553329467773, 84.76483917236328, 140.99722290039062, 56.34513473510742, 61.18817138671875, 48.196102142333984, 35.91091537475586, 125.8998031616211, 103.1183853149414, 35.53615951538086, 163.8963623046875, 24.796178817749023, 22.81646728515625, 143.4669647216797, 49.42945098876953, 63.331825256347656, 61.864471435546875, 35.74053955078125, 188.6639404296875, 44.265594482421875, 182.0699920654297, 68.22329711914062, 93.98783111572266, 69.34320068359375, 25.832138061523438, 126.16040802001953, 165.6515655517578, 53.01414108276367, 78.728515625, 23.022308349609375, 96.46904754638672, 26.112762451171875, 137.57974243164062, 29.828197479248047, 60.54931640625, 149.5697021484375, 26.36187744140625, 130.85360717773438, 148.77777099609375, 133.30047607421875, 32.98232650756836, 66.42115020751953, 42.527679443359375, 104.46697998046875, 239.40167236328125, 194.14317321777344, 20.891103744506836, 26.12152099609375, 190.3034210205078, 141.44879150390625, 63.10807418823242, 42.296592712402344, 75.66714477539062, 70.75405883789062, 38.6370849609375, 41.780731201171875, 95.8851547241211, 47.97587966918945, 44.49896240234375, 159.6826171875, 24.347719192504883, 162.5719451904297, 98.6956787109375, 90.4388427734375, 93.5643539428711, 36.54470443725586, 23.342529296875, 59.697723388671875, 298.92437744140625, 28.65811538696289, 32.4144287109375, 92.67362213134766, 73.78973388671875, 116.30130767822266, 60.13259506225586, 188.5887451171875, 47.1990966796875, 49.0555419921875, 27.921527862548828, 167.16265869140625, 92.14815521240234, 57.062313079833984, 112.09779357910156, 220.2041778564453, 22.882568359375, 25.627138137817383, 35.924285888671875, 26.56341552734375, 156.3437042236328, 129.5615234375, 152.0482940673828, 68.029052734375, 70.16973114013672, 31.739530563354492, 82.7983169555664, 44.7830810546875, 202.50198364257812, 119.624267578125, 138.4279022216797, 32.116455078125, 107.7714614868164, 102.744140625, 55.619964599609375, 31.949951171875, 95.17798614501953, 129.6556854248047, 38.9881477355957, 27.61669921875, 52.3861083984375, 30.893339157104492, 33.14164352416992, 64.08625793457031, 106.40166473388672, 99.7466812133789, 125.05926513671875, 30.78704833984375, 43.98450469970703, 33.175907135009766, 20.380252838134766, 47.27716064453125, 85.15966796875, 181.8283233642578, 85.58158111572266, 61.25625228881836, 33.15350341796875, 57.32675552368164, 177.35794067382812, 110.36959075927734, 188.77212524414062, 72.3949966430664, 78.09769439697266, 35.91407012939453, 170.46311950683594, 136.87562561035156, 189.87718200683594, 30.507614135742188, 77.65605926513672, 120.75880432128906, 54.28863525390625, 153.90286254882812, 62.815887451171875, 192.951904296875, 26.2071533203125, 171.18582153320312, 175.7617950439453, 32.00070571899414, 64.51849365234375, 79.2364273071289, 67.24447631835938, 23.67266845703125, 167.83566284179688, 106.79238891601562, 72.30321502685547, 31.929594039916992, 107.59530639648438, 107.46272277832031, 142.28001403808594, 106.76904296875, 192.8761749267578, 28.770404815673828, 92.38333892822266, 262.8609619140625, 86.27163696289062, 77.76138305664062, 25.4698486328125, 69.90811157226562, 28.387399673461914, 91.807861328125, 54.589149475097656, 54.66701889038086, 99.04936981201172, 48.598514556884766, 81.90293884277344, 95.72859191894531, 68.6190185546875, 19.529266357421875, 80.87871551513672, 186.0628204345703, 49.88446044921875, 198.47085571289062, 90.29424285888672, 100.56047821044922, 102.319091796875, 83.50921630859375, 91.71649169921875, 42.0115966796875, 47.049163818359375, 43.873992919921875, 32.382568359375, 75.9522705078125, 33.15692138671875, 39.1591796875, 61.55810546875, 121.50859832763672, 145.29931640625, 1.2438057661056519, 2.5398173332214355, 3.1084887981414795, 2.620316743850708, 2.358325481414795, 2.6947546005249023, 3.316470146179199, 3.2786450386047363, 1.3016228675842285, 1.8772653341293335, 2.583887815475464, 2.708899974822998, 3.334293842315674, 2.2469217777252197, 2.217414140701294, 2.31067156791687, 2.3029680252075195, 2.163813591003418, 2.8547375202178955, 3.295527935028076, 2.306605339050293, 1.2531403303146362, 2.6231014728546143, 1.9091309309005737, 2.966881036758423, 2.4888970851898193, 2.5124948024749756, 1.6354141235351562, 3.4990124702453613, 3.9007694721221924, 2.4408884048461914, 2.5205392837524414, 1.2186936140060425, 1.056092619895935, 2.2754669189453125, 2.424715280532837, 1.3838852643966675, 2.03279709815979, 2.7213892936706543, 2.3467912673950195, 2.2185792922973633, 4.053046226501465, 1.7088069915771484, 2.793919801712036, 1.3784071207046509, 1.702195405960083, 2.7341156005859375, 1.7569626569747925, 2.4310896396636963, 1.6254037618637085, 2.9039580821990967, 3.2068357467651367, 1.2735670804977417, 3.097803831100464, 2.9816925525665283, 2.32287859916687, 2.7171239852905273, 2.973252773284912, 2.960906982421875, 2.65468692779541, 2.0604240894317627, 1.8872994184494019, 2.0938234329223633, 3.432070732116699, 2.1498522758483887, 2.8758385181427, 2.0875158309936523, 1.985707402229309, 2.1895904541015625, 2.448002815246582, 2.8101322650909424, 1.6336861848831177, 2.8804104328155518, 2.9614288806915283, 3.345273733139038, 2.524137258529663, 1.8902007341384888, 3.3619935512542725, 2.840071678161621, 2.3958511352539062, 2.0062341690063477, 2.5078353881835938, 2.0083045959472656, 1.8975189924240112, 3.1008803844451904, 1.9410947561264038, 2.325751543045044, 2.546595573425293, 3.020808458328247, 2.114280939102173, 2.122830390930176, 1.4844573736190796, 1.6395983695983887, 2.0105972290039062, 3.3675756454467773, 3.0183489322662354, 1.823068380355835, 1.9712480306625366, 2.215517997741699, 1.3807592391967773, 1.6188119649887085, 2.9477319717407227, 1.988606333732605, 2.9180409908294678, 1.8555669784545898, 2.508897542953491, 2.5991432666778564, 1.9081214666366577, 1.387784719467163, 3.3000898361206055, 1.6796501874923706, 2.4467575550079346, 2.4944581985473633, 2.3128409385681152, 1.9782521724700928, 2.1246328353881836, 1.6696603298187256, 2.8613674640655518, 2.25876784324646, 1.5302706956863403, 3.561692237854004, 2.740827798843384, 2.0474812984466553, 2.609808921813965, 3.053838014602661, 1.5082882642745972, 1.1445236206054688, 2.3995585441589355, 1.9005762338638306, 2.4833338260650635, 2.857739210128784, 2.0936028957366943, 2.1721816062927246, 2.8483433723449707, 2.8485515117645264, 1.667427897453308, 2.7014458179473877, 1.9676949977874756, 1.4040021896362305, 2.2642507553100586, 3.040879487991333, 3.000535249710083, 2.9604594707489014, 1.4042409658432007, 2.986638069152832, 2.9204037189483643, 2.5886037349700928, 1.6845693588256836, 2.0705955028533936, 2.1755049228668213, 3.413965940475464, 2.732659339904785, 3.1864428520202637, 1.56474769115448, 2.4464049339294434, 2.0970048904418945, 2.864861488342285, 3.316948175430298, 3.072866439819336, 1.309682011604309, 2.0472216606140137, 2.6637980937957764, 1.9305791854858398, 1.4757184982299805, 2.5154542922973633, 1.5744106769561768, 2.5890185832977295, 2.606247901916504, 2.778886079788208, 3.202524423599243, 3.2830686569213867, 2.316499948501587, 2.6316444873809814, 2.629307746887207, 2.5800273418426514, 2.456641435623169, 2.2042739391326904, 1.9724854230880737, 3.580935478210449, 2.4848544597625732, 2.6333324909210205, 2.9263153076171875, 1.6247755289077759, 3.1905853748321533, 2.7025206089019775, 2.23478627204895, 1.5702086687088013, 1.8320931196212769, 2.359100580215454, 1.60455322265625, 3.148405075073242, 1.6500225067138672, 2.8070569038391113, 2.4733173847198486, 3.262747049331665, 1.67790687084198, 2.1419408321380615, 2.342066526412964, 1.9971657991409302, 2.240537405014038, 1.6964980363845825, 2.920642137527466, 2.2700083255767822, 1.626551628112793, 2.0687811374664307, 3.485846519470215, 2.517704725265503, 2.342236280441284, 1.712172508239746, 3.107003688812256, 1.5987824201583862, 2.4656283855438232, 2.743605375289917, 1.6650131940841675, 1.669228434562683, 3.0539567470550537, 1.3479304313659668, 2.0743818283081055, 2.139047145843506, 2.9691364765167236, 1.3063501119613647, 2.32694149017334, 2.2132275104522705, 2.99210262298584, 2.1843652725219727, 2.382500648498535, 2.2913458347320557, 1.2061249017715454, 2.6582469940185547, 2.949331045150757, 2.7809038162231445, 2.2722890377044678, 1.1877814531326294, 2.836554527282715, 2.4281136989593506, 3.007629871368408, 1.17935311794281, 2.4265618324279785, 2.244950771331787, 2.915875196456909, 2.4800140857696533, 2.83884334564209, 2.589459180831909, 2.444455623626709, 2.0929527282714844, 2.0257954597473145, 1.5373649597167969, 2.204446315765381, 2.6018998622894287, 3.357158660888672, 3.231423854827881, 2.8630402088165283, 2.0720338821411133, 2.2183890342712402, 1.3186882734298706, 1.8085602521896362, 2.3373842239379883, 1.7927961349487305, 2.449134111404419, 1.851454734802246, 2.54946231842041, 2.6893200874328613, 2.6841976642608643, 2.490006446838379, 2.7849740982055664, 2.862919807434082, 3.0412418842315674, 1.579482078552246, 2.0430116653442383, 2.32450008392334, 2.5859527587890625, 2.57975697517395, 3.0206921100616455, 2.925381660461426, 2.520402669906616, 1.9209890365600586, 2.168084144592285, 1.4695786237716675, 3.393771171569824, 2.8348541259765625, 2.9896514415740967, 1.9773893356323242, 3.128340721130371, 2.4723215103149414, 3.0233547687530518, 2.829493284225464, 2.478656768798828, 2.353724241256714, 2.1590700149536133, 1.949764609336853, 1.4174431562423706, 1.0987513065338135, 2.148620367050171, 1.1785904169082642, 2.5817675590515137, 2.504335641860962, 3.5064477920532227, 1.8669272661209106, 2.2572875022888184, 1.7339617013931274, 0.21151049435138702, 0.1973249763250351, 0.2335652858018875, 0.14360201358795166, 0.07986427843570709, 0.1523585319519043, 0.1288476586341858, 0.15079480409622192, 0.1682651937007904, 0.1575993001461029, 0.1757643073797226, 0.13070009648799896, 0.22201885282993317, 0.16453255712985992, 0.17961852252483368, 0.12928521633148193, 0.1950402557849884, 0.11074413359165192, 0.1515221893787384, 0.19931812584400177, 0.19858293235301971, 0.16575652360916138, 0.18605200946331024, 0.1402292102575302, 0.1152435690164566, 0.21580970287322998, 0.08670035749673843, 0.2235768884420395, 0.13483278453350067, 0.1473347693681717, 0.1269756704568863, 0.14928728342056274, 0.210251122713089, 0.1738128662109375, 0.19407768547534943, 0.14615777134895325, 0.1081124097108841, 0.12690995633602142, 0.15764683485031128, 0.17902778089046478, 0.08089349418878555, 0.19704166054725647, 0.18060016632080078, 0.18028002977371216, 0.16898608207702637, 0.18084052205085754, 0.17941951751708984, 0.1912292242050171, 0.10576948523521423, 0.16198787093162537, 0.21972094476222992, 0.2307218313217163, 0.20639975368976593, 0.19387996196746826, 0.13107988238334656, 0.13830970227718353, 0.09851503372192383, 0.09496542811393738, 0.18742652237415314, 0.15703241527080536, 0.1399732530117035, 0.08778355270624161, 0.16558825969696045, 0.08421272039413452, 0.230966255068779, 0.18347515165805817, 0.1928916722536087, 0.1379767507314682, 0.15992560982704163, 0.11430469155311584, 0.18983088433742523, 0.18470783531665802, 0.12491601705551147, 0.20859986543655396, 0.1267298012971878, 0.19777557253837585, 0.2213658094406128, 0.23223716020584106, 0.22932730615139008, 0.16517333686351776, 0.1492515504360199, 0.1736355572938919, 0.13891324400901794, 0.09573957324028015, 0.21824362874031067, 0.17339052259922028, 0.1306942105293274, 0.1801179051399231, 0.13307777047157288, 0.11558500677347183, 0.08170252293348312, 0.11432267725467682, 0.21841859817504883, 0.18802860379219055, 0.19786198437213898, 0.1921621412038803, 0.16343961656093597, 0.18070422112941742, 0.15694625675678253, 0.20562446117401123, 0.19935542345046997, 0.1518193930387497, 0.17567873001098633, 0.1569581925868988, 0.1212608814239502, 0.15211445093154907, 0.12772908806800842, 0.13813869655132294, 0.12355581670999527, 0.11095672100782394, 0.1915629506111145, 0.19269528985023499, 0.13828754425048828, 0.20122748613357544, 0.1417136937379837, 0.19896066188812256, 0.10444942116737366, 0.13340957462787628, 0.11970340460538864, 0.19280309975147247, 0.1451503187417984, 0.16420644521713257, 0.10366492718458176, 0.1504739373922348, 0.15954820811748505, 0.1792420893907547, 0.16800546646118164, 0.1587534248828888, 0.16713383793830872, 0.21166276931762695, 0.18151450157165527, 0.15178292989730835, 0.11383187770843506, 0.1401410698890686, 0.20227956771850586, 0.1219184622168541, 0.1612568199634552, 0.1810874491930008, 0.13830068707466125, 0.2355937510728836, 0.1951160430908203, 0.15052318572998047, 0.06906276196241379, 0.1752946823835373, 0.13243764638900757, 0.26381489634513855, 0.1472502201795578, 0.14589323103427887, 0.20935189723968506, 0.19064961373806, 0.20315700769424438, 0.19381394982337952, 0.1468144804239273, 0.11576711386442184, 0.17256736755371094, 0.16056789457798004, 0.1747037023305893, 0.1374886929988861, 0.15960492193698883, 0.15824994444847107, 0.1623860001564026, 0.12732678651809692, 0.15221428871154785, 0.18902309238910675, 0.09525329619646072, 0.18853217363357544, 0.13239431381225586, 0.11493155360221863, 0.17981727421283722, 0.17009662091732025, 0.177058145403862, 0.1827896386384964, 0.167311429977417, 0.15341562032699585, 0.12148530781269073, 0.12370168417692184, 0.18790923058986664, 0.14569854736328125, 0.237970769405365, 0.23117399215698242, 0.1820117086172104, 0.14784877002239227, 0.14259885251522064, 0.20420081913471222, 0.20764940977096558, 0.1658816635608673, 0.09709654003381729, 0.15985603630542755, 0.12979553639888763, 0.15317341685295105, 0.18732360005378723, 0.24842065572738647, 0.21380376815795898, 0.12904901802539825, 0.1831633597612381, 0.18894712626934052, 0.18047820031642914, 0.16177068650722504, 0.2170598953962326, 0.17206637561321259, 0.15326237678527832, 0.1709362417459488, 0.11893262714147568, 0.15897288918495178, 0.1990056037902832, 0.18836610019207, 0.1842801570892334, 0.17206433415412903, 0.1781402975320816, 0.1645040065050125, 0.1581767499446869, 0.1803971827030182, 0.11541647464036942, 0.17781297862529755, 0.21170973777770996, 0.14271283149719238, 0.21561965346336365, 0.1759158819913864, 0.21304820477962494, 0.18356354534626007, 0.06556681543588638, 0.17416813969612122, 0.11590254306793213, 0.0715884417295456, 0.20561271905899048, 0.22703856229782104, 0.19889946281909943, 0.18453934788703918, 0.1864205002784729, 0.2827276885509491, 0.21710459887981415, 0.19090843200683594, 0.19463962316513062, 0.1253451704978943, 0.12241748720407486, 0.16499321162700653, 0.19258268177509308, 0.2669437825679779, 0.1653016209602356, 0.14028796553611755, 0.10968652367591858, 0.18388095498085022, 0.18507766723632812, 0.17420418560504913, 0.13379120826721191, 0.15525048971176147, 0.2431950569152832, 0.1973687708377838, 0.18617366254329681, 0.14334632456302643, 0.1991233378648758, 0.17960277199745178, 0.1941620260477066, 0.2035965919494629, 0.13403773307800293, 0.1078176349401474, 0.08981597423553467, 0.19348056614398956, 0.18436892330646515, 0.1880445033311844, 0.1255444586277008, 0.12820716202259064, 0.23353232443332672, 0.23786094784736633, 0.1583091914653778, 0.14043189585208893, 0.14919914305210114, 0.16813895106315613, 0.13378074765205383, 0.1436924934387207, 0.13164162635803223, 0.11347077041864395, 0.15938498079776764, 0.23037095367908478, 0.25381529331207275, 0.1842125654220581, 0.18967147171497345, 0.1728893667459488, 0.25236380100250244, 0.2177533060312271, 0.17131301760673523, 0.19261939823627472, 0.18005718290805817, 0.12579306960105896, 0.14034061133861542, 0.12813903391361237, 0.23104941844940186, 0.1219145730137825, 0.10951536148786545, 0.17291106283664703, 0.15387021005153656, 0.17166860401630402, 0.12822188436985016, 0.14033444225788116, 0.16482067108154297, 0.16676506400108337, 0.14072930812835693, 0.1785285472869873, 0.1892702430486679, 0.15753690898418427, 1.195812702178955, 0.8097584843635559, 1.1130268573760986, 1.137841820716858, 1.298941969871521, 1.2113621234893799, 1.0520445108413696, 0.9033830761909485, 1.0382025241851807, 1.1626861095428467, 1.1887471675872803, 0.9524123668670654, 0.7968823313713074, 1.3085458278656006, 1.6686811447143555, 0.7640471458435059, 1.2228507995605469, 1.043257713317871, 1.7887057065963745, 1.192549705505371, 0.5372913479804993, 1.8650890588760376, 1.4703201055526733, 1.287764310836792, 2.0781400203704834, 0.8834307789802551, 1.5615218877792358, 1.6676609516143799, 1.3964849710464478, 1.4404199123382568, 0.9081511497497559, 1.549699068069458, 1.8105344772338867, 1.2455781698226929, 1.3755792379379272, 1.0388069152832031, 1.4036178588867188, 0.9939886331558228, 1.760229468345642, 1.1652840375900269, 1.4199329614639282, 1.3560022115707397, 1.0960019826889038, 1.7501604557037354, 0.7897535562515259, 1.1606558561325073, 0.7645699381828308, 2.0365774631500244, 1.1710127592086792, 1.6992735862731934, 0.9087020754814148, 1.7517772912979126, 1.5474315881729126, 1.2962169647216797, 1.0410467386245728, 0.7092278599739075, 1.486755132675171, 1.1495940685272217, 0.9205031394958496, 1.1857818365097046, 1.134962558746338, 1.7440580129623413, 1.2147325277328491, 0.921528160572052, 1.7572827339172363, 1.3289047479629517, 1.4476003646850586, 0.9891545176506042, 1.0748465061187744, 1.540857195854187, 1.3795019388198853, 0.8761407136917114, 1.5814323425292969, 0.8612846732139587, 1.0050435066223145, 1.1756038665771484, 1.264981746673584, 1.223182201385498, 1.5944589376449585, 1.5345200300216675, 1.3087542057037354, 1.4848902225494385, 1.6550582647323608, 0.7753379940986633, 1.3279893398284912, 1.1654868125915527, 1.072989821434021, 1.4273252487182617, 0.7520809173583984, 1.1424599885940552, 1.553528070449829, 0.8892141580581665, 1.2521898746490479, 0.9558740854263306, 1.140597939491272, 1.1532682180404663, 1.2372798919677734, 1.3540209531784058, 1.4332561492919922, 1.0486056804656982, 2.240875720977783, 1.5913680791854858, 2.000521183013916, 1.1171822547912598, 1.081855297088623, 1.4433785676956177, 1.527823805809021, 0.7060708403587341, 1.1326857805252075, 1.1813035011291504, 1.0452995300292969, 1.3095144033432007, 1.0544307231903076, 1.165792465209961, 1.49041748046875, 0.9498553276062012, 2.0812172889709473, 0.9917080402374268, 0.6782119870185852, 1.406862497329712, 1.9149187803268433, 0.9486918449401855, 1.5045855045318604, 0.9681618809700012, 1.0559455156326294, 1.1389524936676025, 1.4375659227371216, 1.6650316715240479, 2.132594347000122, 0.864145815372467, 1.2939214706420898, 1.3974764347076416, 0.942615807056427, 1.3732059001922607, 0.9241377115249634, 1.5029293298721313, 1.3194130659103394, 1.02070152759552, 0.9261773228645325, 1.362552285194397, 2.14459228515625, 1.5222628116607666, 1.1104977130889893, 1.6379400491714478, 0.930528461933136, 0.748163640499115, 1.6101080179214478, 0.9851967692375183, 1.053788423538208, 2.2691993713378906, 1.250275731086731, 1.712308645248413, 1.1038376092910767, 0.6662308573722839, 0.7379837036132812, 2.1688711643218994, 2.0677435398101807, 2.4676544666290283, 1.425794005393982, 1.3041878938674927, 1.1766622066497803, 1.1428102254867554, 1.1403900384902954, 1.2657759189605713, 0.8652437329292297, 1.3608590364456177, 1.5629152059555054, 0.591058611869812, 1.0758419036865234, 1.0919796228408813, 1.2110623121261597, 0.8228975534439087, 0.6992823481559753, 1.311670184135437, 1.5438052415847778, 1.897064447402954, 1.3759958744049072, 1.2002811431884766, 1.0515235662460327, 1.1362642049789429, 1.280176043510437, 0.46024513244628906, 1.2510117292404175, 0.6633396744728088, 2.3532261848449707, 0.5588406920433044, 1.13473379611969, 1.0645781755447388, 1.3845560550689697, 0.7613716721534729, 1.7436479330062866, 0.6902812123298645, 0.8830921649932861, 0.6424800157546997, 1.163100242614746, 1.0169230699539185, 1.1430425643920898, 1.3151681423187256, 1.465934157371521, 1.1142674684524536, 1.0298749208450317, 1.269039273262024, 0.8377795219421387, 1.545465350151062, 1.0339860916137695, 1.2646982669830322, 1.733297348022461, 1.3493925333023071, 1.407853364944458, 1.527303695678711, 0.8693268895149231, 0.8849431276321411, 0.9138056039810181, 1.1127681732177734, 1.417697548866272, 0.9924612045288086, 1.3527218103408813, 1.5104891061782837, 1.5316895246505737, 1.5210787057876587, 2.141429901123047, 1.8093960285186768, 1.3576889038085938, 1.0142390727996826, 1.3676440715789795, 1.0246589183807373, 1.055144190788269, 0.9099318981170654, 0.5546467304229736, 1.1213806867599487, 1.0522593259811401, 1.2239887714385986, 1.1358363628387451, 0.8527613878250122, 0.760832667350769, 0.966286301612854, 1.223809003829956, 1.2917934656143188, 1.9602314233779907, 1.679736614227295, 1.5121315717697144, 1.7303746938705444, 1.2358901500701904, 1.5712236166000366, 0.9571566581726074, 0.9095568656921387, 1.238625168800354, 0.9818774461746216, 1.1790324449539185, 1.3574937582015991, 1.726946473121643, 2.2654430866241455, 1.4181817770004272, 1.6459789276123047, 1.697404384613037, 1.3797167539596558, 1.875046968460083, 1.9889984130859375, 1.0401012897491455, 1.5671676397323608, 1.567053198814392, 1.338700532913208, 0.9357766509056091, 1.6421127319335938, 1.5106115341186523, 1.3100143671035767, 1.110564112663269, 1.6201814413070679, 1.5669050216674805, 1.2903928756713867, 1.3042287826538086, 1.3140664100646973, 1.4097237586975098, 0.9410061240196228, 1.053134799003601, 0.8731576204299927, 0.8738024830818176, 1.458377480506897, 1.320749044418335, 0.5076284408569336, 1.4738256931304932, 0.7195768356323242, 0.66025710105896, 1.0963046550750732, 0.808946967124939, 1.1996710300445557, 1.4454010725021362, 1.1581593751907349, 1.2517015933990479, 1.3073898553848267, 1.0148344039916992, 1.5247840881347656, 1.0423692464828491, 1.3615881204605103, 0.5972302556037903, 1.2205774784088135, 1.6852302551269531, 0.8758814930915833, 0.8422453999519348, 1.3824752569198608, 47.728271484375, 110.6517333984375, 25.139467239379883, 71.085693359375, 63.5225944519043, 16.976511001586914, 14.91384220123291, 179.2435760498047, 135.04513549804688, 69.502685546875, 179.82640075683594, 168.1512908935547, 95.3661117553711, 201.1240997314453, 98.99102020263672, 31.72589111328125, 104.92729949951172, 71.16105651855469, 37.18459701538086, 50.870452880859375, 106.81766510009766, 35.93349838256836, 240.7581787109375, 31.78179931640625, 144.69732666015625, 32.70770263671875, 136.38192749023438, 110.06623077392578, 27.812255859375, 24.636459350585938, 57.877899169921875, 111.00189208984375, 45.9197998046875, 64.66793823242188, 148.18687438964844, 136.40829467773438, 107.57765197753906, 67.9832763671875, 127.16451263427734, 110.213134765625, 92.4419937133789, 104.6606216430664, 89.4272232055664, 27.03485107421875, 26.914358139038086, 24.229549407958984, 150.3585662841797, 37.91998291015625, 27.832387924194336, 50.8741455078125, 68.25737762451172, 106.22945404052734, 32.21681213378906, 27.83270263671875, 108.76358032226562, 332.44891357421875, 97.71097564697266, 41.04243087768555, 125.20833587646484, 13.193817138671875, 40.58612060546875, 79.10952758789062, 33.76649475097656, 163.16043090820312, 255.22100830078125, 67.88711547851562, 38.20453643798828, 163.71319580078125, 156.109130859375, 92.91986083984375, 205.64553833007812, 31.07879638671875, 160.39805603027344, 80.98028564453125, 42.983455657958984, 47.78738021850586, 155.5170135498047, 34.45953369140625, 31.3000431060791, 51.366943359375, 123.46554565429688, 86.43877410888672, 151.23858642578125, 126.97147369384766, 124.439208984375, 97.74307250976562, 120.7900390625, 69.33214569091797, 197.9578399658203, 34.158939361572266, 44.77142333984375, 91.94298553466797, 173.0387725830078, 144.588623046875, 58.7437744140625, 132.93087768554688, 139.8783721923828, 47.79377746582031, 59.039794921875, 221.5735321044922, 86.48431396484375, 21.930145263671875, 149.03480529785156, 61.26361083984375, 208.9673614501953, 65.108642578125, 23.699371337890625, 45.61492919921875, 188.70225524902344, 63.67732238769531, 85.17869567871094, 120.96524810791016, 40.82305908203125, 35.98284912109375, 35.44261169433594, 26.04840087890625, 172.43405151367188, 32.68568420410156, 51.529510498046875, 69.3055191040039, 114.59761810302734, 88.22029876708984, 180.3203887939453, 97.9501724243164, 80.0550537109375, 87.43566131591797, 86.51089477539062, 185.6725616455078, 36.915592193603516, 45.84588623046875, 83.38427734375, 107.7682876586914, 112.60560607910156, 135.7496795654297, 118.89261627197266, 141.7323760986328, 145.5714111328125, 57.26903533935547, 93.76103973388672, 99.6717529296875, 142.566650390625, 178.6681671142578, 43.0550537109375, 279.4058837890625, 94.58180236816406, 27.8106689453125, 35.114585876464844, 258.7572021484375, 106.02964782714844, 70.5791015625, 146.45152282714844, 34.14179611206055, 94.2816162109375, 189.7142791748047, 25.165931701660156, 32.9661865234375, 118.94760131835938, 38.57977294921875, 65.53353881835938, 100.3616943359375, 69.03059387207031, 151.6271209716797, 24.177919387817383, 127.93806457519531, 115.56912231445312, 43.87696075439453, 161.71221923828125, 38.60438537597656, 96.60347747802734, 56.3670654296875, 127.30864715576172, 117.73495483398438, 28.105497360229492, 164.6912078857422, 162.65020751953125, 59.19476318359375, 111.07530975341797, 64.33888244628906, 50.25558853149414, 38.29486083984375, 133.92294311523438, 99.93338775634766, 131.91888427734375, 48.365535736083984, 90.73018646240234, 91.92774963378906, 64.56574249267578, 134.01910400390625, 74.80734252929688, 29.25433349609375, 80.51184844970703, 132.87896728515625, 44.605438232421875, 97.58785247802734, 144.82864379882812, 39.53944778442383, 112.84671783447266, 76.62483978271484, 65.2826156616211, 97.56439208984375, 122.6130142211914, 36.2237548828125, 150.2101593017578, 157.27859497070312, 35.93375778198242, 127.70586395263672, 47.17604446411133, 81.83880615234375, 106.6702880859375, 95.98763275146484, 109.64224243164062, 25.49188232421875, 142.4306640625, 148.20849609375, 160.02664184570312, 30.02911376953125, 85.63243865966797, 73.14747619628906, 89.52022552490234, 60.282440185546875, 169.1630096435547, 144.6470489501953, 47.499656677246094, 39.1346435546875, 65.26592254638672, 92.31917572021484, 141.49671936035156, 72.43701171875, 40.973690032958984, 43.4351806640625, 206.46018981933594, 94.9355239868164, 60.20459747314453, 82.35767364501953, 17.736785888671875, 247.8408966064453, 136.488037109375, 102.03569793701172, 28.84600830078125, 33.516300201416016, 146.2439727783203, 169.6791534423828, 117.47747802734375, 25.7564697265625, 43.77314376831055, 46.43646240234375, 108.7034912109375, 235.3783416748047, 48.372314453125, 70.23583984375, 160.34201049804688, 111.55802154541016, 143.99403381347656, 111.60150146484375, 141.95974731445312, 175.0634002685547, 144.42234802246094, 116.71630859375, 142.5805206298828, 231.1253662109375, 54.92156982421875, 178.506103515625, 124.07964324951172, 81.43328094482422, 66.5242919921875, 62.28540802001953, 105.30927276611328, 35.0972900390625, 30.309329986572266, 36.069305419921875, 19.54266357421875, 63.501502990722656, 167.92002868652344, 24.9298095703125, 86.03582763671875, 65.09375, 46.59865188598633, 24.730560302734375, 57.35929870605469, 40.30401611328125, 163.00889587402344, 44.48453903198242, 20.718412399291992, 212.70816040039062, 67.28345489501953, 112.51769256591797, 95.91511535644531, 96.47171783447266, 132.13128662109375, 173.734375, 158.04696655273438, 99.03716278076172, 21.82172966003418, 106.34477996826172, 49.58758544921875, 154.9562225341797, 81.01263427734375, 107.03466796875, 73.49069213867188, 100.4356460571289, 1.3326061964035034, 2.2688779830932617, 3.3694427013397217, 2.940800666809082, 2.8512890338897705, 2.9422123432159424, 1.7641304731369019, 2.102320671081543, 1.5056753158569336, 2.1952643394470215, 1.3350952863693237, 3.1068005561828613, 2.426873207092285, 3.6564173698425293, 2.0598764419555664, 3.3002891540527344, 2.1238927841186523, 1.1990385055541992, 1.843648910522461, 1.7701292037963867, 2.61069917678833, 2.3693487644195557, 2.36820125579834, 3.383610486984253, 3.108670473098755, 2.441148281097412, 2.400303840637207, 3.445329189300537, 2.743586301803589, 2.6452646255493164, 3.1179423332214355, 1.9299899339675903, 2.384161949157715, 2.68234920501709, 2.9078705310821533, 3.620913505554199, 1.6703652143478394, 2.395111083984375, 1.7214077711105347, 2.4027254581451416, 2.7317633628845215, 2.836261034011841, 2.1443111896514893, 1.3228445053100586, 2.376673698425293, 2.889727830886841, 2.1817729473114014, 2.919132709503174, 3.3726603984832764, 1.860597848892212, 2.5020904541015625, 2.232165575027466, 1.6998320817947388, 2.8308041095733643, 1.6829568147659302, 3.7397899627685547, 1.8368465900421143, 2.512200355529785, 3.041177272796631, 2.484196662902832, 2.407517433166504, 3.612896680831909, 2.281243324279785, 2.0908384323120117, 2.4726762771606445, 2.3184430599212646, 3.2635087966918945, 1.936204195022583, 1.345155954360962, 2.0591840744018555, 2.311908006668091, 2.0478219985961914, 2.6092212200164795, 3.259134531021118, 1.7654943466186523, 3.247851848602295, 2.0790586471557617, 3.244939088821411, 2.6028332710266113, 2.111314058303833, 2.9821553230285645, 1.8175185918807983, 3.335536479949951, 2.7412805557250977, 2.94608473777771, 3.163999557495117, 1.7612391710281372, 2.0404062271118164, 1.9516149759292603, 2.282841682434082, 2.539787769317627, 2.451462984085083, 2.975867509841919, 2.186195135116577, 1.888857364654541, 1.5849714279174805, 1.9919482469558716, 3.6188230514526367, 1.9824718236923218, 2.723527431488037, 1.8035192489624023, 2.6749818325042725, 3.008251667022705, 1.9586275815963745, 0.9862546324729919, 2.7090728282928467, 2.95219349861145, 2.582834482192993, 2.6294753551483154, 1.785915493965149, 2.027008295059204, 2.746751070022583, 3.5268030166625977, 1.4284905195236206, 1.7722936868667603, 1.1052980422973633, 2.4164135456085205, 1.6575478315353394, 1.950127363204956, 1.698257565498352, 2.983424663543701, 1.7730021476745605, 2.1490795612335205, 2.3123323917388916, 3.351227283477783, 1.4966038465499878, 2.0378267765045166, 2.6261050701141357, 2.558751106262207, 2.3097915649414062, 1.8310335874557495, 1.1212862730026245, 1.5519834756851196, 1.6786248683929443, 1.6242128610610962, 2.9500908851623535, 2.386214256286621, 2.5427045822143555, 2.6107873916625977, 1.5580167770385742, 2.5730643272399902, 2.029395341873169, 1.8645867109298706, 2.4913859367370605, 1.3382112979888916, 2.6196069717407227, 2.5947062969207764, 3.0915658473968506, 3.0362539291381836, 2.7215476036071777, 2.9236743450164795, 2.676886558532715, 1.9546669721603394, 2.090224266052246, 2.1872847080230713, 2.824312686920166, 2.1299257278442383, 2.211552143096924, 1.711609959602356, 2.677281379699707, 1.7781320810317993, 3.3692028522491455, 1.9229403734207153, 3.1661839485168457, 2.719130754470825, 2.157689094543457, 2.0849924087524414, 1.6193575859069824, 3.2309179306030273, 2.3520615100860596, 1.9633458852767944, 1.7937331199645996, 2.348446846008301, 2.8963615894317627, 2.56559157371521, 3.3397305011749268, 2.2624216079711914, 1.7681185007095337, 1.8159579038619995, 3.134101390838623, 1.9348068237304688, 2.0916683673858643, 2.5671417713165283, 3.2863378524780273, 1.9527801275253296, 2.7942419052124023, 1.7349848747253418, 1.5807546377182007, 1.8408440351486206, 2.359616279602051, 2.085169792175293, 2.657587766647339, 2.5482804775238037, 2.3876543045043945, 1.5705190896987915, 2.234389305114746, 1.8745187520980835, 1.5021179914474487, 3.5657708644866943, 3.3866987228393555, 2.705655574798584, 1.7175952196121216, 2.3001670837402344, 3.1649627685546875, 2.1474578380584717, 2.431014060974121, 1.7163985967636108, 2.4751265048980713, 2.189401865005493, 2.8061249256134033, 2.3698434829711914, 2.040827512741089, 2.238131523132324, 1.794398307800293, 3.210474729537964, 2.0841214656829834, 2.977412462234497, 2.60202693939209, 2.928318977355957, 2.157371997833252, 2.9095122814178467, 2.3461809158325195, 2.6184163093566895, 1.6095629930496216, 2.5029165744781494, 1.5303221940994263, 1.8581578731536865, 2.3201403617858887, 2.5939738750457764, 2.7257258892059326, 2.641362190246582, 1.9577418565750122, 2.4905471801757812, 3.862056255340576, 1.6072521209716797, 2.9226596355438232, 1.6994866132736206, 2.0632638931274414, 2.8633487224578857, 2.072174072265625, 1.7197660207748413, 2.132237434387207, 1.7229725122451782, 1.7077627182006836, 2.435570240020752, 2.84805965423584, 1.7741385698318481, 3.0416479110717773, 3.831583261489868, 2.427870750427246, 2.335692882537842, 2.2858216762542725, 1.9770596027374268, 2.2739970684051514, 1.9820367097854614, 2.63017201423645, 2.5149471759796143, 2.3725574016571045, 2.1636571884155273, 2.259382486343384, 2.748223304748535, 1.996343970298767, 2.9093387126922607, 2.7066240310668945, 1.4318668842315674, 3.6140336990356445, 3.005070686340332, 2.6872012615203857, 2.4536285400390625, 2.739489793777466, 2.9760830402374268, 3.3424317836761475, 1.7223598957061768, 1.8141084909439087, 1.6859389543533325, 2.383906126022339, 2.004300594329834, 2.269465446472168, 1.6007046699523926, 1.6522331237792969, 3.751917839050293, 1.9247525930404663, 2.7981584072113037, 1.4208250045776367, 3.5137884616851807, 2.623562812805176, 1.8333114385604858, 2.1819515228271484, 1.8705010414123535, 3.382589101791382, 2.3007447719573975, 2.558040142059326, 2.3670918941497803, 2.533919095993042, 1.8191040754318237, 3.6846587657928467, 1.571381688117981, 3.0380265712738037, 1.6359307765960693, 2.431852102279663, 0.1496608853340149, 0.1707065999507904, 0.186719611287117, 0.16812081634998322, 0.23857076466083527, 0.11735658347606659, 0.196053609251976, 0.20971086621284485, 0.16479484736919403, 0.17321431636810303, 0.1651497632265091, 0.13480812311172485, 0.2008139044046402, 0.15804173052310944, 0.15958142280578613, 0.157293900847435, 0.18822532892227173, 0.10350099205970764, 0.25657597184181213, 0.15208542346954346, 0.15399646759033203, 0.21928927302360535, 0.1015465259552002, 0.19884160161018372, 0.08450154960155487, 0.1502341479063034, 0.1292361170053482, 0.12004751712083817, 0.1794552356004715, 0.19736972451210022, 0.14019495248794556, 0.15503917634487152, 0.19503699243068695, 0.20025548338890076, 0.1344703733921051, 0.16852831840515137, 0.14548611640930176, 0.16287162899971008, 0.17147216200828552, 0.20825403928756714, 0.11852388828992844, 0.20759537816047668, 0.1492607295513153, 0.13260993361473083, 0.1569034606218338, 0.1646929532289505, 0.14896850287914276, 0.19677305221557617, 0.16807375848293304, 0.15094979107379913, 0.1618315428495407, 0.17652779817581177, 0.1874971091747284, 0.19239623844623566, 0.1602354645729065, 0.19386577606201172, 0.2263283133506775, 0.15782515704631805, 0.13291388750076294, 0.12066847831010818, 0.23740600049495697, 0.17895156145095825, 0.19658534228801727, 0.15473611652851105, 0.20612353086471558, 0.15139064192771912, 0.1682635247707367, 0.15948161482810974, 0.15280334651470184, 0.1530970185995102, 0.15155944228172302, 0.19425632059574127, 0.12150786072015762, 0.2101123332977295, 0.16815941035747528, 0.1269376128911972, 0.21714355051517487, 0.21044643223285675, 0.13843272626399994, 0.12769128382205963, 0.1857420653104782, 0.12942971289157867, 0.16731472313404083, 0.19654609262943268, 0.15755949914455414, 0.12352216243743896, 0.10894984006881714, 0.17464542388916016, 0.13462617993354797, 0.13711820542812347, 0.17481300234794617, 0.16126836836338043, 0.12296729534864426, 0.11235538125038147, 0.2329077273607254, 0.19164292514324188, 0.16844145953655243, 0.16969908773899078, 0.16199469566345215, 0.18150080740451813, 0.17330417037010193, 0.25959619879722595, 0.17022374272346497, 0.15003401041030884, 0.16694480180740356, 0.1880211979150772, 0.21793124079704285, 0.15011297166347504, 0.19656115770339966, 0.19089297950267792, 0.17216041684150696, 0.10376535356044769, 0.12010541558265686, 0.26499971747398376, 0.13368616998195648, 0.19411277770996094, 0.055687349289655685, 0.1193452998995781, 0.14523063600063324, 0.17580454051494598, 0.1785632073879242, 0.15151965618133545, 0.11556705087423325, 0.17419470846652985, 0.17437684535980225, 0.1819588840007782, 0.18636870384216309, 0.1798875778913498, 0.13765399158000946, 0.14897264540195465, 0.18082229793071747, 0.13245965540409088, 0.18550139665603638, 0.155324786901474, 0.14611254632472992, 0.1556539237499237, 0.16836291551589966, 0.1487627774477005, 0.11140063405036926, 0.13705730438232422, 0.17766006290912628, 0.17557907104492188, 0.1691197156906128, 0.14933425188064575, 0.1921902745962143, 0.19497431814670563, 0.16230270266532898, 0.15179572999477386, 0.13701549172401428, 0.1209898367524147, 0.14751103520393372, 0.2248317301273346, 0.13350160419940948, 0.1522541344165802, 0.13244907557964325, 0.20092721283435822, 0.21269480884075165, 0.13839219510555267, 0.14032568037509918, 0.1196460872888565, 0.10445654392242432, 0.10371270775794983, 0.1543126106262207, 0.1672777682542801, 0.17151038348674774, 0.1621900349855423, 0.2630407214164734, 0.10676133632659912, 0.17644575238227844, 0.10281825065612793, 0.07310815155506134, 0.14461703598499298, 0.15976601839065552, 0.1110735684633255, 0.1339082270860672, 0.1519051492214203, 0.15459443628787994, 0.22998987138271332, 0.13030865788459778, 0.2216479778289795, 0.1479870229959488, 0.1309775561094284, 0.16167159378528595, 0.15075373649597168, 0.17244774103164673, 0.12021112442016602, 0.16527976095676422, 0.11047324538230896, 0.1421269327402115, 0.1830630898475647, 0.10594554990530014, 0.21131205558776855, 0.1304861456155777, 0.24419546127319336, 0.22989481687545776, 0.20335185527801514, 0.14624172449111938, 0.20068395137786865, 0.15807786583900452, 0.1462453454732895, 0.16420242190361023, 0.14369918406009674, 0.19957418739795685, 0.1600176990032196, 0.20931613445281982, 0.15083271265029907, 0.19182835519313812, 0.16237609088420868, 0.18961036205291748, 0.19038479030132294, 0.1706542670726776, 0.1999073326587677, 0.12875860929489136, 0.20087550580501556, 0.16268089413642883, 0.1350965052843094, 0.12242313474416733, 0.20220819115638733, 0.1510687619447708, 0.13307511806488037, 0.1713314801454544, 0.1796460896730423, 0.1290128082036972, 0.28725096583366394, 0.12860256433486938, 0.118323914706707, 0.12487422674894333, 0.22501632571220398, 0.21146038174629211, 0.14511071145534515, 0.14684566855430603, 0.22896885871887207, 0.14391152560710907, 0.26960042119026184, 0.20900310575962067, 0.1885523498058319, 0.2324753850698471, 0.15787212550640106, 0.19358131289482117, 0.15185411274433136, 0.11343955993652344, 0.14076800644397736, 0.1576714664697647, 0.24338574707508087, 0.17173263430595398, 0.15606941282749176, 0.14511127769947052, 0.10018041729927063, 0.15803347527980804, 0.1722477376461029, 0.12059015035629272, 0.16062535345554352, 0.1442592591047287, 0.15726099908351898, 0.1551954448223114, 0.15635588765144348, 0.1331518292427063, 0.15094828605651855, 0.15855132043361664, 0.13377876579761505, 0.19619949162006378, 0.18437595665454865, 0.2085408717393875, 0.15323229134082794, 0.1512935906648636, 0.18639548122882843, 0.13538525998592377, 0.23667781054973602, 0.1682005673646927, 0.19792601466178894, 0.11513839662075043, 0.15579108893871307, 0.16812436282634735, 0.114593505859375, 0.1658172905445099, 0.0911494642496109, 0.16007834672927856, 0.17748206853866577, 0.1552325040102005, 0.14348101615905762, 0.17826047539710999, 0.1457040160894394, 0.11968819051980972, 0.16181115806102753, 0.16472499072551727, 0.20363885164260864, 0.2335953265428543, 0.15570199489593506, 0.14304229617118835, 0.11850333958864212, 0.15445177257061005, 0.20443248748779297, 0.22148633003234863, 0.18259572982788086, 0.11543355882167816, 0.2545166611671448, 0.1682945042848587, 0.15485644340515137, 0.14267025887966156, 0.1411495953798294, 0.9637662768363953, 1.0762603282928467, 1.7092560529708862, 1.3585193157196045, 1.3356144428253174, 1.039597988128662, 1.1042978763580322, 1.2475529909133911, 1.3251872062683105, 1.3850252628326416, 1.7516793012619019, 2.063300848007202, 1.3588365316390991, 1.2329013347625732, 1.2870891094207764, 1.4868662357330322, 0.7221928834915161, 1.3060972690582275, 1.7059721946716309, 1.3736034631729126, 1.5081576108932495, 1.0738555192947388, 2.0612387657165527, 1.6294714212417603, 1.0932444334030151, 1.5916706323623657, 0.885657012462616, 1.3747928142547607, 0.8634321689605713, 1.2764467000961304, 1.1490163803100586, 0.8538097739219666, 1.084311604499817, 1.0617258548736572, 1.4046283960342407, 1.6753630638122559, 1.028709888458252, 0.667807936668396, 0.9269928336143494, 1.6906732320785522, 1.5410760641098022, 1.6525588035583496, 2.2847399711608887, 1.0830265283584595, 1.4199450016021729, 1.515830397605896, 1.9180700778961182, 2.40938138961792, 1.1214323043823242, 0.863091230392456, 0.8522483706474304, 1.3484485149383545, 1.1775542497634888, 1.356583833694458, 1.1573339700698853, 1.8365764617919922, 0.8352016806602478, 1.1990249156951904, 0.887751042842865, 1.143052339553833, 1.7281551361083984, 0.963824987411499, 1.4779415130615234, 1.6366207599639893, 1.6890140771865845, 1.066481113433838, 1.8935312032699585, 1.3879339694976807, 1.3467904329299927, 1.8238903284072876, 0.773624837398529, 1.5954033136367798, 1.380651831626892, 0.9823649525642395, 2.380981922149658, 0.9655909538269043, 1.1287184953689575, 0.7298022508621216, 1.597001314163208, 0.9745885133743286, 1.7039040327072144, 1.3061574697494507, 0.9042359590530396, 0.9611374735832214, 0.9962807893753052, 0.9719651341438293, 1.2676194906234741, 1.3187847137451172, 1.927820086479187, 1.2417813539505005, 1.315005898475647, 0.9264271259307861, 1.43950617313385, 1.027549147605896, 1.1574008464813232, 0.9160229563713074, 1.0810608863830566, 1.4473539590835571, 1.5132211446762085, 1.1944993734359741, 1.014582633972168, 1.8556652069091797, 1.2134438753128052, 0.93169766664505, 1.919492483139038, 1.8881723880767822, 1.6706652641296387, 2.1967012882232666, 0.9990848898887634, 1.6693017482757568, 1.7096527814865112, 1.5457804203033447, 1.0470362901687622, 0.8965977430343628, 2.706866502761841, 1.727828025817871, 0.7931080460548401, 1.1967625617980957, 0.8911348581314087, 1.197488784790039, 0.9585663676261902, 1.3207454681396484, 1.646688461303711, 2.014936685562134, 1.0518196821212769, 0.8410407900810242, 0.9721192717552185, 1.5515626668930054, 1.3194150924682617, 1.551953673362732, 1.2695993185043335, 1.3570826053619385, 0.7501274943351746, 1.3670915365219116, 1.4990507364273071, 1.2391560077667236, 0.8230841755867004, 1.2988817691802979, 1.1592727899551392, 1.4125769138336182, 1.3650175333023071, 1.3736181259155273, 1.8206286430358887, 1.505102515220642, 1.6697040796279907, 2.1183276176452637, 1.6256678104400635, 1.5230343341827393, 1.284338355064392, 1.4083139896392822, 1.7648779153823853, 1.3490819931030273, 1.1059437990188599, 2.5137956142425537, 0.8837478160858154, 1.4940013885498047, 1.7201626300811768, 0.8906874656677246, 1.0476425886154175, 1.7185900211334229, 1.3801424503326416, 1.8006905317306519, 1.1919207572937012, 1.6711548566818237, 1.7307548522949219, 1.3626152276992798, 1.5131288766860962, 1.3332748413085938, 1.667003870010376, 1.6677923202514648, 1.3790773153305054, 1.546857476234436, 0.9369031190872192, 1.778487205505371, 1.3461647033691406, 1.6130105257034302, 1.696380615234375, 1.3268091678619385, 0.7071051597595215, 1.195363163948059, 1.8741041421890259, 0.6402711272239685, 0.9448643922805786, 0.7589476704597473, 0.8533585667610168, 1.574643850326538, 0.8035928010940552, 0.9852652549743652, 1.5579088926315308, 1.245366096496582, 1.0513420104980469, 1.5177074670791626, 1.8527170419692993, 1.41720449924469, 1.1432499885559082, 0.8846504092216492, 1.4557180404663086, 1.5205814838409424, 0.9820661544799805, 1.9419670104980469, 1.3482742309570312, 0.8801450729370117, 1.217081069946289, 0.9643233418464661, 1.3696050643920898, 0.716547966003418, 1.3878339529037476, 0.8655295372009277, 1.514574646949768, 1.425779104232788, 1.1796674728393555, 0.9754689335823059, 1.2871171236038208, 2.3615291118621826, 2.2912700176239014, 1.151397705078125, 1.4311338663101196, 1.0908160209655762, 0.6578930616378784, 1.5350176095962524, 2.275604724884033, 1.2784779071807861, 1.4861719608306885, 1.4022356271743774, 1.450295090675354, 1.1087820529937744, 1.505064606666565, 0.89715176820755, 1.6287606954574585, 1.3818696737289429, 1.5601787567138672, 2.411771535873413, 1.4042224884033203, 0.7066947817802429, 1.4296356439590454, 1.1290431022644043, 1.2764078378677368, 1.574275016784668, 1.8081430196762085, 1.1567074060440063, 1.3252813816070557, 1.138831615447998, 1.0192618370056152, 1.6233019828796387, 1.447548508644104, 1.1762490272521973, 1.6430654525756836, 1.0944926738739014, 1.6309159994125366, 1.4408771991729736, 0.9540268778800964, 1.4869942665100098, 1.6410287618637085, 1.456140160560608, 1.1794664859771729, 1.391460657119751, 1.4070473909378052, 1.1382880210876465, 1.242667555809021, 1.1879725456237793, 1.5409109592437744, 1.606138825416565, 1.6698921918869019, 0.8377858400344849, 0.6860693097114563, 1.6824668645858765, 0.8489443063735962, 1.5412248373031616, 0.9707944989204407, 1.9004312753677368, 1.6772997379302979, 1.4679012298583984, 2.6545562744140625, 1.6792736053466797, 1.715417742729187, 1.227995753288269, 1.2334544658660889, 1.003963589668274, 1.6061697006225586, 1.2206436395645142, 1.0509989261627197, 1.754311203956604, 0.8409242630004883, 1.597819447517395, 2.717527389526367, 1.544655680656433, 1.2505961656570435, 1.6279642581939697, 1.0645991563796997, 2.340315103530884, 1.6681143045425415, 2.199767827987671, 1.1637229919433594, 0.8478614687919617, 0.9653610587120056, 1.104372501373291, 1.3295660018920898, 1.4844557046890259, 1.0217660665512085, 1.4172531366348267, 141.7289581298828, 45.19155502319336, 76.45751953125, 125.85125732421875, 27.073627471923828, 172.92855834960938, 73.73979949951172, 101.01079559326172, 50.35546875, 69.79508972167969, 214.2508544921875, 198.5599365234375, 123.30184936523438, 71.58685302734375, 108.73011779785156, 37.268821716308594, 37.06657028198242, 25.85076904296875, 36.262699127197266, 43.316219329833984, 66.1322021484375, 26.7491455078125, 227.81626892089844, 158.46592712402344, 47.43519592285156, 200.1808624267578, 41.59197998046875, 38.423431396484375, 147.7952880859375, 67.01532745361328, 86.86737060546875, 110.45668029785156, 124.48089599609375, 30.04290771484375, 66.01839447021484, 153.92466735839844, 32.71554946899414, 66.35319519042969, 71.63217163085938, 109.30511474609375, 25.55976104736328, 140.60067749023438, 120.64959716796875, 36.11481475830078, 154.142578125, 143.24072265625, 28.641996383666992, 256.79046630859375, 45.432342529296875, 56.37605285644531, 31.499696731567383, 181.2913055419922, 151.56442260742188, 28.547025680541992, 116.38626861572266, 62.70376968383789, 132.14366149902344, 80.1007080078125, 104.30511474609375, 164.74359130859375, 31.17327880859375, 131.94342041015625, 50.7193603515625, 116.56351470947266, 44.15589141845703, 220.50537109375, 50.50706100463867, 22.1131591796875, 280.34002685546875, 65.70110321044922, 186.0592803955078, 164.63682556152344, 134.8438262939453, 171.8669891357422, 134.857421875, 54.068904876708984, 341.0132751464844, 51.25262451171875, 88.52651977539062, 218.1502227783203, 112.25792694091797, 35.74090576171875, 96.61136627197266, 148.03466796875, 100.1851806640625, 79.16217803955078, 93.92925262451172, 126.5594711303711, 155.94178771972656, 59.75093460083008, 19.4796142578125, 27.960956573486328, 172.17327880859375, 104.45252990722656, 146.6720428466797, 124.04046630859375, 35.922119140625, 181.4276123046875, 31.026126861572266, 201.0717315673828, 137.005615234375, 114.32755279541016, 64.75800323486328, 164.12042236328125, 54.221405029296875, 29.7247314453125, 103.02655029296875, 103.61942291259766, 89.14913177490234, 106.88107299804688, 27.111774444580078, 130.41650390625, 179.40869140625, 58.86252975463867, 185.8982391357422, 40.193695068359375, 92.3163070678711, 138.02645874023438, 333.4613342285156, 47.33685302734375, 183.37803649902344, 89.53214263916016, 51.15651321411133, 31.14617919921875, 138.04425048828125, 118.517578125, 116.24982452392578, 138.38754272460938, 96.671142578125, 101.5068130493164, 138.48936462402344, 92.12744140625, 23.334178924560547, 160.3494873046875, 72.8031005859375, 109.802490234375, 136.69923400878906, 96.36602020263672, 42.44158935546875, 165.01422119140625, 150.3311309814453, 117.11333465576172, 59.4954833984375, 42.951263427734375, 97.06449127197266, 62.34736251831055, 75.7674560546875, 27.521730422973633, 119.60076904296875, 91.06269073486328, 127.50101470947266, 133.32980346679688, 65.2235107421875, 269.49658203125, 53.67818069458008, 107.66020202636719, 121.91020965576172, 60.4627685546875, 140.52423095703125, 72.31423950195312, 179.71214294433594, 23.214813232421875, 150.03929138183594, 56.3372802734375, 125.769775390625, 164.28956604003906, 230.35113525390625, 58.64042663574219, 49.8043212890625, 116.241455078125, 116.42743682861328, 113.963623046875, 24.4888916015625, 215.47412109375, 145.27206420898438, 70.641845703125, 432.25982666015625, 119.55709075927734, 47.201717376708984, 96.61087799072266, 67.65689086914062, 92.4365234375, 175.37425231933594, 57.07688522338867, 116.50395965576172, 20.92041015625, 84.9407958984375, 130.438232421875, 97.03701782226562, 39.99376678466797, 28.813438415527344, 63.70613479614258, 92.66047668457031, 239.43968200683594, 33.34186553955078, 96.19853973388672, 42.9794921875, 20.216796875, 173.42979431152344, 122.24718475341797, 65.41797637939453, 74.06069946289062, 238.6942596435547, 74.48292541503906, 47.61858367919922, 95.77204132080078, 100.45037841796875, 18.36440658569336, 136.44139099121094, 120.86712646484375, 40.39656448364258, 42.8721923828125, 182.8714599609375, 116.3616943359375, 139.623291015625, 194.0670928955078, 51.61050796508789, 88.05786895751953, 113.44412994384766, 220.9964141845703, 133.17100524902344, 249.974365234375, 32.05357360839844, 56.59296798706055, 132.01849365234375, 59.92287826538086, 30.552581787109375, 109.25003814697266, 159.60235595703125, 24.39813232421875, 36.29241943359375, 25.017391204833984, 96.4327621459961, 23.7259521484375, 109.04046630859375, 22.332582473754883, 105.152099609375, 69.7039566040039, 29.6112060546875, 27.379486083984375, 96.40399169921875, 84.49302673339844, 52.86603927612305, 80.03339385986328, 36.441650390625, 80.04033660888672, 113.98212432861328, 148.6319122314453, 44.579345703125, 162.65692138671875, 50.1729736328125, 46.966400146484375, 25.813871383666992, 34.32536697387695, 350.44659423828125, 86.610595703125, 125.32173919677734, 64.55221557617188, 100.42658996582031, 20.0006046295166, 176.472412109375, 44.6351318359375, 74.1075439453125, 31.575889587402344, 50.59339904785156, 90.13105010986328, 159.03077697753906, 48.4053955078125, 138.45399475097656, 121.36553192138672, 33.88031005859375, 77.47462463378906, 26.9674015045166, 86.44552612304688, 70.59109497070312, 75.1937255859375, 93.71862030029297, 36.889644622802734, 110.2557601928711, 95.57328033447266, 27.021484375, 45.901214599609375, 261.1678771972656, 114.22769927978516, 124.55821990966797, 81.01499938964844, 50.29330062866211, 111.38253021240234, 72.54238891601562, 65.77422332763672, 47.6776123046875, 36.99381637573242, 165.01910400390625, 138.37615966796875, 36.344886779785156, 90.57318115234375, 33.38078689575195, 116.19961547851562, 194.0853729248047, 150.9407958984375, 1.6552568674087524, 1.9648771286010742, 1.6928378343582153, 2.5583086013793945, 0.9983360171318054, 2.2178945541381836, 2.372711181640625, 1.4592026472091675, 2.7044975757598877, 2.21822452545166, 2.9962565898895264, 1.3766202926635742, 3.9394290447235107, 2.262354612350464, 1.216935396194458, 3.5505483150482178, 3.1392929553985596, 2.070958137512207, 1.7682991027832031, 2.3514013290405273, 1.652146577835083, 3.1825180053710938, 3.5702009201049805, 3.3414058685302734, 2.3621015548706055, 2.3411853313446045, 2.661452054977417, 1.8394378423690796, 4.139366149902344, 2.2523794174194336, 1.7552196979522705, 1.8430935144424438, 2.4500932693481445, 2.008516788482666, 1.3274277448654175, 3.1420934200286865, 3.3042519092559814, 2.9129350185394287, 1.4337340593338013, 2.5012130737304688, 2.4991588592529297, 2.6500771045684814, 1.741921305656433, 2.4037699699401855, 1.672475814819336, 1.8014599084854126, 2.434293270111084, 1.607192039489746, 3.5417051315307617, 1.4982002973556519, 2.0702733993530273, 2.859389543533325, 2.452498435974121, 1.8061742782592773, 3.6714837551116943, 1.3841220140457153, 1.9397697448730469, 1.4116851091384888, 3.222874641418457, 3.4255504608154297, 2.8474090099334717, 3.228875160217285, 3.1725823879241943, 3.40261173248291, 2.9430131912231445, 2.6784374713897705, 2.614149808883667, 3.083510637283325, 2.4581689834594727, 3.025195360183716, 3.1103923320770264, 2.10176944732666, 2.708292245864868, 2.9605553150177, 2.5072450637817383, 2.7439661026000977, 1.7968331575393677, 2.3642935752868652, 2.2680234909057617, 2.461289405822754, 1.5667208433151245, 3.30130934715271, 1.1156548261642456, 1.7710884809494019, 2.38397216796875, 2.1773135662078857, 2.8323090076446533, 2.76078724861145, 2.5719006061553955, 1.3630790710449219, 2.9870121479034424, 2.3119497299194336, 2.926893472671509, 1.713871717453003, 2.747169017791748, 2.4368762969970703, 2.4642069339752197, 1.8210821151733398, 2.221632957458496, 1.62016761302948, 1.6798603534698486, 2.071368455886841, 1.7808964252471924, 2.376969337463379, 3.5405073165893555, 2.07010555267334, 1.303090214729309, 2.354405403137207, 3.66400146484375, 2.048129081726074, 1.9816428422927856, 2.3527133464813232, 2.943467378616333, 2.553176164627075, 3.0965373516082764, 1.9713060855865479, 3.6501150131225586, 2.23437237739563, 1.2889164686203003, 1.664729118347168, 2.1482973098754883, 1.7516411542892456, 2.2714788913726807, 2.9631683826446533, 1.774208903312683, 2.039229393005371, 2.9954564571380615, 2.218923807144165, 1.6790398359298706, 2.636629819869995, 2.77677059173584, 2.4623167514801025, 2.5287909507751465, 2.1536145210266113, 2.7373955249786377, 2.542616844177246, 2.1205215454101562, 3.0384037494659424, 2.4960343837738037, 3.1769096851348877, 1.6059606075286865, 1.6439623832702637, 1.6657363176345825, 3.534573793411255, 2.9051201343536377, 1.674580454826355, 3.6495561599731445, 1.7066984176635742, 3.0230822563171387, 2.475545644760132, 2.480846405029297, 2.136521339416504, 2.61568284034729, 2.8184304237365723, 1.9264593124389648, 3.140326976776123, 3.0573949813842773, 2.869318723678589, 2.108034372329712, 1.4060806035995483, 3.124905824661255, 2.5478525161743164, 1.5535231828689575, 1.9796862602233887, 1.6842163801193237, 3.2736151218414307, 2.2612905502319336, 2.443814277648926, 1.0671037435531616, 2.0295019149780273, 2.078341484069824, 4.212706565856934, 1.7020708322525024, 3.1295764446258545, 2.1585569381713867, 2.3582091331481934, 3.3498716354370117, 2.21726131439209, 2.9248454570770264, 2.5420641899108887, 3.282151460647583, 1.4306408166885376, 2.6358494758605957, 3.405865430831909, 2.6739342212677, 1.8856611251831055, 2.6374354362487793, 3.3193767070770264, 2.5983476638793945, 4.0564680099487305, 2.931851625442505, 2.42611026763916, 3.7023231983184814, 1.735526442527771, 3.066605806350708, 2.0986242294311523, 2.7227494716644287, 1.9260244369506836, 3.5100371837615967, 2.1210145950317383, 2.075714111328125, 2.582381248474121, 2.347975015640259, 1.898238182067871, 2.6682350635528564, 3.169644594192505, 2.082866668701172, 0.9788293242454529, 1.6134569644927979, 2.567420244216919, 2.331163167953491, 2.997267961502075, 3.1301567554473877, 2.0889694690704346, 1.746881365776062, 1.7986373901367188, 1.7423467636108398, 1.308229923248291, 2.8636670112609863, 2.6716971397399902, 2.0843915939331055, 2.1725645065307617, 1.919249176979065, 2.9015748500823975, 3.862971782684326, 2.8702032566070557, 2.96496319770813, 2.8088645935058594, 3.2916674613952637, 1.7687829732894897, 2.9457857608795166, 2.7377688884735107, 2.09368896484375, 1.859108805656433, 1.6723241806030273, 2.284594774246216, 2.3398187160491943, 3.301304817199707, 1.2479888200759888, 1.720682978630066, 3.025071382522583, 2.3000097274780273, 1.4431383609771729, 2.5367822647094727, 1.2787736654281616, 2.4987633228302, 2.903149366378784, 2.1494383811950684, 2.083706855773926, 3.79955792427063, 2.071603298187256, 1.538826823234558, 2.313901901245117, 3.453808546066284, 1.8417408466339111, 3.315035820007324, 3.966177225112915, 1.8176085948944092, 1.919645071029663, 2.790828227996826, 1.910790205001831, 1.926249623298645, 2.3092901706695557, 3.1158974170684814, 2.8954288959503174, 1.8031196594238281, 2.829078197479248, 2.4746179580688477, 1.8313952684402466, 3.0021026134490967, 2.5615646839141846, 2.7216482162475586, 1.634601354598999, 3.6457793712615967, 2.394191265106201, 3.5998473167419434, 2.3595471382141113, 1.6962426900863647, 1.7740898132324219, 2.298150062561035, 2.2824013233184814, 1.9434843063354492, 2.0672998428344727, 2.7644436359405518, 1.7177881002426147, 2.3151090145111084, 1.4695005416870117, 2.1379454135894775, 2.4061081409454346, 1.7669271230697632, 2.085615873336792, 2.2485058307647705, 3.0171144008636475, 1.4032697677612305, 2.8252885341644287, 3.0760834217071533, 2.1669867038726807, 1.7086495161056519, 2.877195358276367, 3.626481294631958, 0.20693737268447876, 0.19555816054344177, 0.23728112876415253, 0.255648672580719, 0.11764755100011826, 0.17827755212783813, 0.13736115396022797, 0.14017003774642944, 0.15222688019275665, 0.16284939646720886, 0.23609495162963867, 0.21087892353534698, 0.1359359472990036, 0.12559100985527039, 0.21059665083885193, 0.1969980150461197, 0.15519246459007263, 0.1624746322631836, 0.16728217899799347, 0.15996724367141724, 0.14854322373867035, 0.18321047723293304, 0.1810583621263504, 0.17732185125350952, 0.13368983566761017, 0.20851300656795502, 0.16404922306537628, 0.09163042157888412, 0.1894998848438263, 0.13768799602985382, 0.08116000890731812, 0.1643647402524948, 0.20447379350662231, 0.18652436137199402, 0.1268007904291153, 0.10841280966997147, 0.2462618350982666, 0.15240587294101715, 0.10078897327184677, 0.22848224639892578, 0.1408098042011261, 0.11884559690952301, 0.15812206268310547, 0.11290083825588226, 0.26333945989608765, 0.15700703859329224, 0.16713321208953857, 0.16023144125938416, 0.16872930526733398, 0.20185916125774384, 0.17148715257644653, 0.15841588377952576, 0.18913745880126953, 0.17348612844944, 0.23170654475688934, 0.17645297944545746, 0.1390371322631836, 0.13584408164024353, 0.14915548264980316, 0.16110940277576447, 0.11940401792526245, 0.16831664741039276, 0.191874697804451, 0.21009238064289093, 0.21196314692497253, 0.19335709512233734, 0.18785060942173004, 0.1398695707321167, 0.17325706779956818, 0.1972179412841797, 0.16620475053787231, 0.04344409704208374, 0.12622110545635223, 0.15833888947963715, 0.1329512596130371, 0.17109474539756775, 0.15432392060756683, 0.1555289775133133, 0.17291083931922913, 0.20412983000278473, 0.12662170827388763, 0.1818239986896515, 0.12736773490905762, 0.17308564484119415, 0.15998779237270355, 0.1993565857410431, 0.14360100030899048, 0.08680140227079391, 0.22837293148040771, 0.16480235755443573, 0.14450164139270782, 0.10629448294639587, 0.15488453209400177, 0.20624879002571106, 0.12793011963367462, 0.15308669209480286, 0.15502311289310455, 0.1306275576353073, 0.18443244695663452, 0.20694659650325775, 0.15849359333515167, 0.17146705090999603, 0.15083874762058258, 0.19145061075687408, 0.08593852818012238, 0.22408229112625122, 0.12775924801826477, 0.18243594467639923, 0.1736508160829544, 0.11145582050085068, 0.18730533123016357, 0.1565152257680893, 0.20622380077838898, 0.19343051314353943, 0.20852558314800262, 0.17789681255817413, 0.2189040184020996, 0.12358943372964859, 0.16576488316059113, 0.14784406125545502, 0.17360995709896088, 0.1408524513244629, 0.11769258230924606, 0.14333748817443848, 0.14939244091510773, 0.14917978644371033, 0.1656671166419983, 0.18221889436244965, 0.16132037341594696, 0.17280852794647217, 0.16424736380577087, 0.1824321299791336, 0.12571237981319427, 0.14996136724948883, 0.17827139794826508, 0.1913919448852539, 0.17592279613018036, 0.21630889177322388, 0.16852469742298126, 0.1775646209716797, 0.12750546634197235, 0.13923679292201996, 0.1658325493335724, 0.15798428654670715, 0.20374375581741333, 0.18478205800056458, 0.15177685022354126, 0.2057374119758606, 0.1855437010526657, 0.15752798318862915, 0.13770055770874023, 0.19984588027000427, 0.17009933292865753, 0.09193120896816254, 0.24534961581230164, 0.17829568684101105, 0.21067343652248383, 0.18798820674419403, 0.21037501096725464, 0.16260938346385956, 0.223418191075325, 0.11028970777988434, 0.22388172149658203, 0.1485336720943451, 0.17081141471862793, 0.11574898660182953, 0.22556836903095245, 0.1918250173330307, 0.15112359821796417, 0.2064986526966095, 0.18943855166435242, 0.12268444150686264, 0.10122790932655334, 0.12899120151996613, 0.15238390862941742, 0.17819732427597046, 0.19595667719841003, 0.1847260296344757, 0.18376758694648743, 0.17165398597717285, 0.2045246809720993, 0.18038654327392578, 0.18429003655910492, 0.19136326014995575, 0.20158308744430542, 0.1381308138370514, 0.13755396008491516, 0.20603401958942413, 0.16263669729232788, 0.16605931520462036, 0.1617170125246048, 0.18506444990634918, 0.2169203758239746, 0.21131551265716553, 0.12506307661533356, 0.20086367428302765, 0.19357779622077942, 0.20155006647109985, 0.1464257538318634, 0.19348113238811493, 0.14720460772514343, 0.15656989812850952, 0.25204578042030334, 0.14762361347675323, 0.16553550958633423, 0.1262863576412201, 0.12966857850551605, 0.17057842016220093, 0.14647109806537628, 0.23187708854675293, 0.18063926696777344, 0.10879296064376831, 0.10109394788742065, 0.1414991021156311, 0.23072044551372528, 0.07447852939367294, 0.14574626088142395, 0.18091563880443573, 0.16331082582473755, 0.14558137953281403, 0.12624049186706543, 0.14409005641937256, 0.19892771542072296, 0.1723290979862213, 0.18748122453689575, 0.20550166070461273, 0.24321341514587402, 0.19422662258148193, 0.11948686093091965, 0.1739470213651657, 0.1767081469297409, 0.15340927243232727, 0.09304223954677582, 0.15713442862033844, 0.1228291466832161, 0.1327904909849167, 0.1187388002872467, 0.13726672530174255, 0.15079575777053833, 0.2052810937166214, 0.24486739933490753, 0.22850489616394043, 0.11966698616743088, 0.14368517696857452, 0.16242477297782898, 0.154035285115242, 0.15425796806812286, 0.18811437487602234, 0.1152908131480217, 0.1374632567167282, 0.21199753880500793, 0.14793454110622406, 0.12758509814739227, 0.15034818649291992, 0.14539127051830292, 0.1953112781047821, 0.14004652202129364, 0.2203308790922165, 0.13893869519233704, 0.17186152935028076, 0.16287483274936676, 0.1984560191631317, 0.14108143746852875, 0.19397832453250885, 0.12245120853185654, 0.16755712032318115, 0.1239934116601944, 0.14237622916698456, 0.13486255705356598, 0.20435741543769836, 0.12192249298095703, 0.06268155574798584, 0.1614198237657547, 0.1934974044561386, 0.1613105684518814, 0.18347099423408508, 0.10297267884016037, 0.20295900106430054, 0.19999007880687714, 0.20542636513710022, 0.1808430701494217, 0.14640818536281586, 0.0962085872888565, 0.12660551071166992, 0.18281836807727814, 0.19507980346679688, 0.14466094970703125, 0.12039311230182648, 0.14042077958583832, 0.23348283767700195, 0.1785753220319748, 0.17363394796848297, 0.1623939424753189, 0.1033892035484314, 0.17914466559886932, 0.16782008111476898, 0.11213190853595734, 0.2392098605632782, 0.1956804096698761, 0.25130602717399597, 2.09121036529541, 0.8868845701217651, 1.0846444368362427, 1.5432442426681519, 1.6671127080917358, 1.274480938911438, 2.238145351409912, 1.07480788230896, 1.1546008586883545, 1.62643301486969, 1.3907963037490845, 1.1190980672836304, 0.652206540107727, 1.2973130941390991, 1.2931480407714844, 1.0418777465820312, 1.3854315280914307, 1.619920253753662, 1.0556695461273193, 1.5199860334396362, 1.89317786693573, 0.7468294501304626, 0.9564220905303955, 1.6410354375839233, 1.4782907962799072, 1.6904754638671875, 1.3818212747573853, 1.9291635751724243, 1.4493944644927979, 1.1563291549682617, 0.8675639033317566, 1.5868393182754517, 1.5419625043869019, 1.357338547706604, 1.0665146112442017, 0.9096848964691162, 1.4352279901504517, 1.0585932731628418, 1.2076375484466553, 1.1227575540542603, 1.7096933126449585, 1.6616454124450684, 1.8840916156768799, 1.7816004753112793, 1.6416113376617432, 1.8574661016464233, 1.3239409923553467, 1.6931698322296143, 1.0793821811676025, 1.4404754638671875, 2.081852912902832, 1.0701582431793213, 1.0743263959884644, 1.2913436889648438, 1.4997094869613647, 2.1289966106414795, 1.4255962371826172, 1.3693084716796875, 1.5493433475494385, 1.1749604940414429, 1.391526460647583, 1.8554253578186035, 1.136195182800293, 1.3713566064834595, 1.3605754375457764, 1.3308717012405396, 1.43702232837677, 0.7556955814361572, 1.655398964881897, 1.3580846786499023, 1.218735933303833, 1.151747703552246, 1.5816013813018799, 0.7053253054618835, 1.0848605632781982, 1.1334949731826782, 1.0033783912658691, 1.3843170404434204, 1.4321084022521973, 1.4601168632507324, 1.7442902326583862, 1.6399739980697632, 1.9409226179122925, 1.6890395879745483, 1.4739818572998047, 1.4776420593261719, 1.7270252704620361, 1.2113971710205078, 1.5980981588363647, 1.197919249534607, 2.268563747406006, 1.7926183938980103, 1.532705307006836, 0.7854094505310059, 0.8010261058807373, 1.173229694366455, 0.9847028851509094, 1.658919334411621, 1.6752874851226807, 1.488417625427246, 1.4567464590072632, 1.197645664215088, 1.6601943969726562, 0.876429557800293, 1.6177418231964111, 1.1950364112854004, 2.270609140396118, 1.3103021383285522, 1.770827293395996, 1.3398164510726929, 1.4540287256240845, 1.4905391931533813, 2.2443580627441406, 0.787118136882782, 1.5297847986221313, 1.0123788118362427, 1.7335395812988281, 1.8195098638534546, 1.1168371438980103, 1.4518755674362183, 2.0477242469787598, 1.2562971115112305, 0.6462084650993347, 1.3527593612670898, 1.1109970808029175, 1.6605913639068604, 1.4412384033203125, 1.6093952655792236, 1.3155258893966675, 1.4449785947799683, 1.2830593585968018, 1.199126124382019, 2.5292367935180664, 1.6391099691390991, 0.941633939743042, 0.9451509714126587, 1.021274209022522, 1.16373872756958, 0.6749076843261719, 1.2218537330627441, 1.783367395401001, 1.753077507019043, 1.0884889364242554, 1.3264755010604858, 1.038352370262146, 2.1262946128845215, 1.6576699018478394, 1.1011964082717896, 1.0981051921844482, 1.5019830465316772, 1.4863463640213013, 1.2506300210952759, 1.914149284362793, 1.8406424522399902, 1.391125202178955, 1.080275058746338, 1.371614694595337, 0.8139283061027527, 1.1180903911590576, 1.898693323135376, 0.8472008109092712, 1.2044423818588257, 1.4246574640274048, 1.641166090965271, 0.766771137714386, 0.9899495244026184, 1.5772573947906494, 0.8080840110778809, 1.2489712238311768, 1.8286632299423218, 1.2805569171905518, 1.455831527709961, 1.954404592514038, 1.189530611038208, 0.8360969424247742, 0.9816901683807373, 1.1664695739746094, 1.270067811012268, 1.6984926462173462, 2.088470935821533, 1.2179772853851318, 1.6881645917892456, 0.7359237670898438, 1.855627417564392, 0.9633181691169739, 1.112940788269043, 1.1371811628341675, 1.0547878742218018, 1.123254418373108, 1.2368149757385254, 1.2632287740707397, 1.3189257383346558, 1.6791948080062866, 0.9481156468391418, 0.6333308219909668, 0.9305287599563599, 1.829068899154663, 1.043790340423584, 1.664223313331604, 1.3478214740753174, 1.2876935005187988, 1.234644889831543, 0.9290916323661804, 2.11314058303833, 0.9285430908203125, 1.0465680360794067, 2.1962943077087402, 1.4430580139160156, 1.1358075141906738, 1.3135138750076294, 0.9852046966552734, 1.1719825267791748, 1.2297472953796387, 1.800159215927124, 1.7831652164459229, 1.3158595561981201, 1.471491813659668, 2.1283154487609863, 1.0355815887451172, 0.9047019481658936, 0.814683735370636, 1.1161751747131348, 1.0414183139801025, 1.4593403339385986, 1.7832012176513672, 1.3071218729019165, 0.4789186716079712, 1.7144454717636108, 0.6073746085166931, 1.2206356525421143, 1.619920253753662, 0.8078575134277344, 0.9815360903739929, 1.5759819746017456, 1.4394854307174683, 0.9551386833190918, 1.4757241010665894, 1.3506704568862915, 0.820054829120636, 1.3886345624923706, 1.725272536277771, 0.9476863145828247, 0.7550447583198547, 1.5332982540130615, 1.8420969247817993, 0.944157063961029, 1.1477067470550537, 1.136759638786316, 1.384851336479187, 1.7392959594726562, 1.5692437887191772, 1.3072509765625, 1.2809780836105347, 1.795005440711975, 1.4930120706558228, 1.132887601852417, 0.9692692160606384, 0.9957229495048523, 0.9992744326591492, 1.2354927062988281, 1.1902961730957031, 1.1114578247070312, 1.8037961721420288, 1.1898479461669922, 1.9523855447769165, 2.031464099884033, 1.8435026407241821, 2.3013768196105957, 1.6370528936386108, 1.0705174207687378, 2.042663812637329, 1.2137476205825806, 1.9449306726455688, 1.303133249282837, 0.9130034446716309, 1.421866774559021, 1.2168320417404175, 1.0314993858337402, 0.7335306406021118, 0.91291743516922, 0.7929723858833313, 1.396456241607666, 1.6732412576675415, 1.8056100606918335, 0.649910569190979, 1.575905442237854, 1.5487101078033447, 1.4882562160491943, 1.370904803276062, 1.622314453125, 1.5188674926757812, 1.1563650369644165, 1.5965954065322876, 0.9995167255401611, 1.3831478357315063, 0.5682907104492188, 1.4761053323745728, 0.9437066316604614, 1.8105251789093018, 1.2422118186950684, 57.81898880004883, 197.71800231933594, 124.701171875, 155.990234375, 175.2156982421875, 172.98583984375, 24.873056411743164, 81.69119262695312, 68.53533935546875, 77.36994171142578, 115.91608428955078, 24.01276397705078, 70.37939453125, 22.77682876586914, 46.998046875, 62.115447998046875, 165.7689208984375, 45.83319091796875, 214.4872283935547, 127.54698181152344, 159.96766662597656, 41.80935287475586, 48.76971435546875, 150.986328125, 101.641357421875, 163.85693359375, 102.7938232421875, 88.91831970214844, 208.4246826171875, 87.43792724609375, 86.1448745727539, 110.55560302734375, 128.73199462890625, 60.6355094909668, 47.55989456176758, 201.1717071533203, 70.55340576171875, 58.47565841674805, 114.64824676513672, 95.29300689697266, 96.50395965576172, 113.15931701660156, 121.8623046875, 126.05033111572266, 84.19933319091797, 179.05816650390625, 89.12283325195312, 47.172821044921875, 76.26132202148438, 78.06061553955078, 38.13531494140625, 229.0434112548828, 52.02186584472656, 58.13467788696289, 264.38775634765625, 272.5823059082031, 233.7071075439453, 92.88141632080078, 52.44192123413086, 118.18547821044922, 110.29656982421875, 20.435791015625, 48.91142654418945, 82.14571380615234, 111.223388671875, 80.984619140625, 172.5741729736328, 134.67864990234375, 71.9508056640625, 71.86297607421875, 138.15628051757812, 51.31399154663086, 29.477540969848633, 54.207366943359375, 98.96295928955078, 160.10072326660156, 95.0892562866211, 60.28103256225586, 260.5048522949219, 37.67304229736328, 25.275381088256836, 128.4640655517578, 170.3971405029297, 40.00788116455078, 86.63167572021484, 24.99357032775879, 147.58721923828125, 139.82958984375, 57.89228439331055, 124.54936981201172, 125.18244934082031, 125.47046661376953, 52.929832458496094, 109.62738037109375, 90.69802856445312, 49.3614501953125, 86.8317642211914, 120.81063842773438, 38.213565826416016, 53.927093505859375, 80.267333984375, 143.42955017089844, 202.66384887695312, 101.01714324951172, 111.775390625, 75.07293701171875, 110.49837493896484, 139.289794921875, 98.9422607421875, 149.59117126464844, 138.71636962890625, 36.07769775390625, 28.874174118041992, 45.726131439208984, 41.80034637451172, 30.570194244384766, 52.38823699951172, 116.78946685791016, 161.86346435546875, 114.37257385253906, 101.193359375, 32.084686279296875, 36.72085952758789, 25.911102294921875, 202.7735137939453, 88.698486328125, 50.923954010009766, 213.5594482421875, 198.65855407714844, 92.5539321899414, 36.78640365600586, 218.4652862548828, 106.62982177734375, 23.247621536254883, 138.53651428222656, 71.40296936035156, 54.41732406616211, 197.4138946533203, 81.99142456054688, 67.46932983398438, 67.41387176513672, 119.27404022216797, 178.6351776123047, 105.15008544921875, 82.412841796875, 92.36244201660156, 193.81613159179688, 95.88468170166016, 199.5764923095703, 22.38411521911621, 217.36045837402344, 104.56084442138672, 44.00885772705078, 100.77120971679688, 76.26016235351562, 64.22783660888672, 38.41278076171875, 43.97841262817383, 81.9754867553711, 61.663021087646484, 75.740966796875, 87.747802734375, 22.385616302490234, 119.6327133178711, 125.97621154785156, 41.12784194946289, 195.81976318359375, 195.32095336914062, 120.1009521484375, 101.49574279785156, 162.20623779296875, 191.23643493652344, 117.15962982177734, 103.00384521484375, 210.8396759033203, 99.26444244384766, 32.370941162109375, 62.65460205078125, 67.47067260742188, 152.560791015625, 125.45169830322266, 203.0624237060547, 36.013885498046875, 114.97855377197266, 58.43888854980469, 65.89857482910156, 55.14443588256836, 88.49432373046875, 92.63153076171875, 207.18264770507812, 152.286376953125, 175.61148071289062, 117.62078857421875, 23.223241806030273, 95.35784912109375, 106.83692932128906, 98.26128387451172, 170.7212677001953, 169.25335693359375, 73.58049011230469, 200.67453002929688, 92.6962661743164, 68.58859252929688, 50.680213928222656, 107.33368682861328, 132.13304138183594, 154.71620178222656, 155.37249755859375, 25.091796875, 190.42376708984375, 148.3483123779297, 38.74171447753906, 118.36894989013672, 84.03900146484375, 80.78591918945312, 24.166776657104492, 46.1983642578125, 34.65185546875, 44.1082763671875, 119.9274673461914, 95.02129364013672, 173.6359405517578, 89.986328125, 34.506103515625, 91.6455078125, 107.09320068359375, 47.15773391723633, 82.55284881591797, 29.2159423828125, 27.084503173828125, 93.73709106445312, 32.17108154296875, 108.92609405517578, 24.945966720581055, 155.49798583984375, 151.53326416015625, 57.7626838684082, 50.90822982788086, 130.04644775390625, 82.87933349609375, 86.75382995605469, 112.75222778320312, 74.77275848388672, 163.4115447998047, 133.457763671875, 79.02590942382812, 53.859100341796875, 83.09402465820312, 20.44464874267578, 117.60595703125, 57.24198532104492, 180.94046020507812, 78.18463897705078, 126.1978988647461, 23.297607421875, 42.1259765625, 31.619384765625, 88.68331909179688, 43.902435302734375, 58.92924499511719, 58.76711654663086, 159.15286254882812, 93.02153778076172, 118.4550552368164, 79.42057800292969, 62.33343505859375, 155.33522033691406, 53.85516357421875, 111.26162719726562, 230.40005493164062, 121.66524505615234, 28.320648193359375, 60.24518585205078, 63.56093978881836, 24.52239990234375, 98.75935363769531, 144.99664306640625, 121.09600067138672, 124.24464416503906, 29.956092834472656, 97.38983154296875, 139.8619384765625, 37.04030990600586, 83.9417724609375, 82.07023620605469, 21.000028610229492, 202.2583770751953, 117.67796325683594, 37.12946319580078, 177.15902709960938, 29.22283935546875, 99.67679595947266, 39.454288482666016, 131.50299072265625, 86.08351135253906, 33.11655044555664, 157.2218780517578, 26.28587532043457, 38.473602294921875, 169.27587890625, 2.05757737159729, 3.0729522705078125, 3.4449880123138428, 2.225050926208496, 2.6304478645324707, 1.7560241222381592, 2.8240673542022705, 1.9603039026260376, 1.7959297895431519, 2.831943988800049, 1.4581397771835327, 1.6815900802612305, 2.6835644245147705, 2.936823606491089, 3.16369366645813, 2.43927264213562, 1.9048889875411987, 2.386939287185669, 2.982009172439575, 2.949355363845825, 1.53497314453125, 1.6393799781799316, 2.0769553184509277, 3.9423828125, 2.2827258110046387, 2.087419271469116, 2.1098108291625977, 2.008715867996216, 1.5123223066329956, 1.9863073825836182, 2.5045671463012695, 2.9391262531280518, 1.901326060295105, 2.510162353515625, 1.510294795036316, 3.090489387512207, 3.0396032333374023, 1.9883909225463867, 2.1786162853240967, 1.8747392892837524, 1.527668833732605, 1.8512792587280273, 2.151803731918335, 2.066300868988037, 2.58389949798584, 2.4790163040161133, 3.3755292892456055, 2.5358948707580566, 2.033351182937622, 1.3604726791381836, 2.5269055366516113, 2.6963701248168945, 2.092442512512207, 3.0505034923553467, 1.0857046842575073, 1.322063684463501, 1.855820894241333, 2.221858263015747, 1.4174648523330688, 1.5465339422225952, 2.4832708835601807, 3.059556245803833, 1.992920994758606, 2.438076972961426, 1.698695182800293, 2.3375020027160645, 2.2450456619262695, 2.3534655570983887, 1.7070417404174805, 2.947352170944214, 1.5062683820724487, 3.032757520675659, 1.9791573286056519, 3.1957104206085205, 1.4840255975723267, 2.24312686920166, 1.6466479301452637, 2.133355140686035, 2.0188207626342773, 2.589836359024048, 2.576481819152832, 2.4141664505004883, 1.5809423923492432, 1.812697410583496, 1.302669644355774, 2.6786155700683594, 3.0301060676574707, 2.530032157897949, 1.4976377487182617, 2.424757957458496, 3.7960526943206787, 1.7720996141433716, 2.525186777114868, 2.526585578918457, 1.958003044128418, 1.7819693088531494, 2.1138715744018555, 1.2683581113815308, 2.314812660217285, 2.9731242656707764, 3.2585461139678955, 2.4754762649536133, 3.356982946395874, 3.0475916862487793, 3.8704042434692383, 1.4299975633621216, 3.466575860977173, 2.2099809646606445, 2.677666664123535, 2.0028281211853027, 1.8398079872131348, 1.911948800086975, 1.3453550338745117, 2.6510701179504395, 3.445925712585449, 1.870233416557312, 2.0810976028442383, 1.7970892190933228, 2.97733211517334, 3.2760581970214844, 1.6414724588394165, 1.441785216331482, 2.1015846729278564, 3.029115915298462, 2.204174518585205, 2.3070502281188965, 2.3099710941314697, 2.189662456512451, 3.4748733043670654, 2.1862382888793945, 2.577533006668091, 2.0390138626098633, 2.008878707885742, 2.0985803604125977, 2.6726653575897217, 1.7209069728851318, 1.8928604125976562, 1.8391408920288086, 1.9135890007019043, 1.3172171115875244, 2.197242259979248, 2.754798173904419, 4.002291679382324, 2.8366153240203857, 2.4645566940307617, 2.305682420730591, 2.0537939071655273, 2.7291977405548096, 1.5336655378341675, 2.9537858963012695, 2.569700241088867, 2.8348119258880615, 3.7970073223114014, 2.7013638019561768, 3.3646016120910645, 1.9300413131713867, 3.46652889251709, 2.558176279067993, 2.7419915199279785, 1.7583893537521362, 2.02618145942688, 1.940773844718933, 2.367865562438965, 2.6798510551452637, 1.7452011108398438, 1.5251295566558838, 2.0248374938964844, 1.9594357013702393, 2.5657589435577393, 2.3298044204711914, 1.7479432821273804, 1.8475104570388794, 3.570563316345215, 1.6835912466049194, 2.171459197998047, 2.530601978302002, 1.6237963438034058, 2.6450488567352295, 2.317013740539551, 2.8422038555145264, 3.3585216999053955, 2.1495046615600586, 1.905967116355896, 2.0481674671173096, 1.7801586389541626, 2.3702001571655273, 3.594238758087158, 2.8363659381866455, 3.12253475189209, 2.4118242263793945, 2.572995185852051, 2.692563772201538, 2.0832877159118652, 3.1808793544769287, 1.721899390220642, 1.880812644958496, 2.085965394973755, 3.601969003677368, 3.160231351852417, 3.007866859436035, 1.5334709882736206, 2.418398380279541, 1.466019868850708, 2.2244925498962402, 2.5283584594726562, 2.464934825897217, 3.60695743560791, 1.534743309020996, 2.84505295753479, 2.9666969776153564, 2.5594968795776367, 2.429321765899658, 1.8812174797058105, 3.3571062088012695, 1.864572286605835, 2.826470375061035, 2.740084171295166, 4.466252326965332, 2.9378998279571533, 2.823842763900757, 2.7133281230926514, 2.8105053901672363, 1.7313413619995117, 2.4822638034820557, 2.079716682434082, 2.8144500255584717, 1.7516393661499023, 2.9260876178741455, 2.079423666000366, 3.12541127204895, 1.8794313669204712, 3.213320732116699, 1.6089736223220825, 1.7660530805587769, 1.790908932685852, 2.7602715492248535, 2.084249258041382, 2.4818010330200195, 2.570878267288208, 2.1911745071411133, 2.9847803115844727, 2.6966793537139893, 1.9114867448806763, 1.7851723432540894, 2.792193651199341, 3.622056245803833, 2.5154359340667725, 2.0455007553100586, 2.6284379959106445, 3.1288061141967773, 3.838644027709961, 2.1304800510406494, 2.162163734436035, 1.517282485961914, 2.7403595447540283, 3.7319304943084717, 1.7886124849319458, 2.441091299057007, 2.2239928245544434, 2.9865481853485107, 3.13350772857666, 1.7388263940811157, 2.0657670497894287, 2.856644868850708, 2.0766265392303467, 2.4314706325531006, 1.4477207660675049, 3.6555397510528564, 2.357682228088379, 2.1233248710632324, 1.72337806224823, 2.5560128688812256, 2.1610498428344727, 2.323380470275879, 2.552377700805664, 2.0862531661987305, 1.8197640180587769, 3.0462963581085205, 3.105585813522339, 2.1163721084594727, 2.118607997894287, 2.8842947483062744, 2.8059170246124268, 1.895345687866211, 2.1558713912963867, 3.340548515319824, 1.6006383895874023, 2.8351082801818848, 2.984668016433716, 2.1838197708129883, 2.330369234085083, 2.948115825653076, 1.134745478630066, 3.2306888103485107, 1.6656159162521362, 3.44254207611084, 2.6680550575256348, 2.2749407291412354, 1.8157432079315186, 2.5740294456481934, 0.1625325232744217, 0.14952845871448517, 0.2242337316274643, 0.16846823692321777, 0.17125259339809418, 0.1849338859319687, 0.2115902155637741, 0.17360934615135193, 0.14710697531700134, 0.17504432797431946, 0.13258172571659088, 0.19939008355140686, 0.09725037217140198, 0.14077506959438324, 0.18198946118354797, 0.16240094602108002, 0.16245540976524353, 0.13591057062149048, 0.19323985278606415, 0.14030639827251434, 0.11317756772041321, 0.14436833560466766, 0.0790969505906105, 0.1649198830127716, 0.15146911144256592, 0.14244122803211212, 0.18737851083278656, 0.13950151205062866, 0.12613974511623383, 0.18317492306232452, 0.2106916308403015, 0.22534774243831635, 0.19612590968608856, 0.17668543756008148, 0.14767199754714966, 0.2000526785850525, 0.22951333224773407, 0.19631624221801758, 0.19200237095355988, 0.11903595924377441, 0.12671396136283875, 0.21229588985443115, 0.23406489193439484, 0.13649962842464447, 0.11325152963399887, 0.2097182273864746, 0.20590628683567047, 0.14807812869548798, 0.16470077633857727, 0.1641751229763031, 0.11482425779104233, 0.19197508692741394, 0.23463279008865356, 0.20186574757099152, 0.16255606710910797, 0.19782039523124695, 0.1579173505306244, 0.18540602922439575, 0.1705363243818283, 0.14041194319725037, 0.11911174654960632, 0.0916530191898346, 0.10413773357868195, 0.16155722737312317, 0.16068121790885925, 0.16495642066001892, 0.1361599862575531, 0.1181928962469101, 0.17984580993652344, 0.20135624706745148, 0.1825924515724182, 0.13059435784816742, 0.26872381567955017, 0.2178855687379837, 0.20002062618732452, 0.12315236032009125, 0.21013355255126953, 0.15588021278381348, 0.14945261180400848, 0.18898025155067444, 0.16875357925891876, 0.1702682077884674, 0.14995798468589783, 0.18905480206012726, 0.134812593460083, 0.1835535317659378, 0.2062508761882782, 0.20626841485500336, 0.12150728702545166, 0.2252533733844757, 0.1639709174633026, 0.20334523916244507, 0.20080167055130005, 0.14102083444595337, 0.20283101499080658, 0.10167726874351501, 0.08115459233522415, 0.11428216844797134, 0.23244620859622955, 0.18514148890972137, 0.09955240041017532, 0.20486600697040558, 0.0753883421421051, 0.21555280685424805, 0.17643597722053528, 0.16246074438095093, 0.198661208152771, 0.16242873668670654, 0.13576684892177582, 0.25457343459129333, 0.14265203475952148, 0.15519089996814728, 0.19170069694519043, 0.12644341588020325, 0.20789004862308502, 0.19235263764858246, 0.18549911677837372, 0.14976751804351807, 0.15024487674236298, 0.1925266534090042, 0.1889016479253769, 0.20666244626045227, 0.21769696474075317, 0.1998744159936905, 0.13483166694641113, 0.1637117862701416, 0.19236735999584198, 0.17283229529857635, 0.1599566638469696, 0.17689912021160126, 0.2248445302248001, 0.1904062032699585, 0.1560828685760498, 0.16053903102874756, 0.1626683622598648, 0.19464632868766785, 0.17496852576732635, 0.12281862646341324, 0.23405331373214722, 0.14118704199790955, 0.10096516460180283, 0.17587357759475708, 0.1364867389202118, 0.1643357276916504, 0.19943471252918243, 0.18085715174674988, 0.18118701875209808, 0.13389424979686737, 0.22513411939144135, 0.1477404534816742, 0.14566925168037415, 0.14897722005844116, 0.15777237713336945, 0.13688813149929047, 0.2242184430360794, 0.2135729044675827, 0.1283869594335556, 0.19085906445980072, 0.22611430287361145, 0.1705988347530365, 0.2592639625072479, 0.18272006511688232, 0.22794993221759796, 0.240609809756279, 0.13638857007026672, 0.2284802943468094, 0.14654380083084106, 0.21404814720153809, 0.19345951080322266, 0.19188754260540009, 0.21032321453094482, 0.17498807609081268, 0.187153160572052, 0.13216817378997803, 0.18417991697788239, 0.14607840776443481, 0.15353578329086304, 0.11621487140655518, 0.21096576750278473, 0.146646186709404, 0.19689543545246124, 0.15217705070972443, 0.06662596017122269, 0.16751296818256378, 0.21805526316165924, 0.11329784244298935, 0.1581020951271057, 0.2185887098312378, 0.18363872170448303, 0.09946759790182114, 0.13629058003425598, 0.16085192561149597, 0.1932133585214615, 0.25287681818008423, 0.22885535657405853, 0.18555614352226257, 0.19207556545734406, 0.1743246167898178, 0.18725283443927765, 0.13774710893630981, 0.12598183751106262, 0.17915767431259155, 0.14063100516796112, 0.16337861120700836, 0.18851199746131897, 0.23231208324432373, 0.1468249261379242, 0.14714962244033813, 0.13786444067955017, 0.10805904120206833, 0.13582555949687958, 0.171773299574852, 0.16873370110988617, 0.10234534740447998, 0.16621452569961548, 0.1858024150133133, 0.19865643978118896, 0.1777379959821701, 0.15211977064609528, 0.19408456981182098, 0.1386018991470337, 0.16689762473106384, 0.16256292164325714, 0.2271811068058014, 0.15159492194652557, 0.19092769920825958, 0.21454554796218872, 0.19865120947360992, 0.19026704132556915, 0.2288743555545807, 0.2054557055234909, 0.13028131425380707, 0.19293279945850372, 0.18291011452674866, 0.21024161577224731, 0.13736377656459808, 0.11867017298936844, 0.18222735822200775, 0.17877444624900818, 0.12960217893123627, 0.12851500511169434, 0.15426485240459442, 0.14411772787570953, 0.18055999279022217, 0.16289196908473969, 0.15127545595169067, 0.17397482693195343, 0.13543863594532013, 0.18534520268440247, 0.1719166487455368, 0.1532527655363083, 0.15558113157749176, 0.17431437969207764, 0.17878997325897217, 0.10279110074043274, 0.20425359904766083, 0.21210284531116486, 0.21420058608055115, 0.11375019699335098, 0.1260722577571869, 0.169666588306427, 0.19550685584545135, 0.2067619413137436, 0.1527397632598877, 0.09288295358419418, 0.2089470624923706, 0.14854541420936584, 0.15400806069374084, 0.11377763748168945, 0.13160495460033417, 0.1660512089729309, 0.20849120616912842, 0.12242843210697174, 0.16714011132717133, 0.21761639416217804, 0.25699785351753235, 0.16451019048690796, 0.2417479306459427, 0.19055068492889404, 0.1380220502614975, 0.18000765144824982, 0.11553652584552765, 0.18869011104106903, 0.16916003823280334, 0.1364801526069641, 0.16253045201301575, 0.19326935708522797, 0.17915712296962738, 0.1981237381696701, 0.2001068890094757, 0.18959876894950867, 0.15787151455879211, 0.1926887482404709, 0.21207958459854126, 0.1279570460319519, 0.1928398311138153, 0.1953953355550766, 0.13567018508911133, 0.15540540218353271, 0.13575413823127747, 1.7974767684936523, 2.143944263458252, 1.43508780002594, 1.3172787427902222, 1.3216280937194824, 1.317271113395691, 1.750658631324768, 1.528334617614746, 1.5557855367660522, 1.3017367124557495, 1.5906410217285156, 1.544055461883545, 0.936802327632904, 0.9687950015068054, 1.1897180080413818, 1.1794708967208862, 1.0884515047073364, 2.3486428260803223, 1.1639869213104248, 2.022106885910034, 1.0077508687973022, 1.4256185293197632, 1.6714600324630737, 1.7741961479187012, 0.8329128623008728, 1.0836082696914673, 2.2022111415863037, 1.3062331676483154, 1.3902088403701782, 2.1548240184783936, 1.4330798387527466, 1.698691964149475, 0.8076658248901367, 1.1388163566589355, 1.0521646738052368, 1.7284493446350098, 2.3247525691986084, 1.2629868984222412, 1.825325608253479, 1.0878660678863525, 2.1319222450256348, 1.49334716796875, 0.8959492444992065, 1.6910793781280518, 1.4718676805496216, 1.245718240737915, 1.3500090837478638, 1.4256463050842285, 0.9329037070274353, 1.4384384155273438, 1.113518238067627, 1.4123039245605469, 1.3046636581420898, 1.3436214923858643, 1.6109081506729126, 0.9570679068565369, 1.7603272199630737, 2.4144253730773926, 1.2472975254058838, 0.841225266456604, 1.1908550262451172, 1.6098384857177734, 1.5507653951644897, 1.3439233303070068, 1.4576895236968994, 2.1148717403411865, 1.0832617282867432, 1.5690100193023682, 1.1622155904769897, 1.001490592956543, 1.1946172714233398, 1.4980400800704956, 0.9340112805366516, 1.194493055343628, 1.9480113983154297, 1.2434957027435303, 1.709653615951538, 1.191215991973877, 1.4097036123275757, 2.321601152420044, 2.452287435531616, 1.17025887966156, 0.9589215517044067, 1.0650825500488281, 1.803845763206482, 1.2179696559906006, 1.4948610067367554, 1.5465103387832642, 1.9135971069335938, 1.6537072658538818, 1.0124075412750244, 1.3679016828536987, 2.181279182434082, 1.664945363998413, 1.3040703535079956, 1.538537859916687, 1.7366385459899902, 1.6262327432632446, 1.362021803855896, 1.0706232786178589, 1.5060555934906006, 1.3857568502426147, 1.3514105081558228, 1.3376901149749756, 1.1733578443527222, 1.8578957319259644, 1.416239619255066, 1.6151103973388672, 1.6928011178970337, 1.4684560298919678, 0.9930286407470703, 1.3796310424804688, 1.3564127683639526, 1.1601150035858154, 1.167004108428955, 1.583266258239746, 1.8778676986694336, 0.7592440843582153, 1.4993127584457397, 1.3438018560409546, 1.076569676399231, 1.0801185369491577, 1.2870135307312012, 1.4278429746627808, 1.0936464071273804, 1.0251147747039795, 1.6891487836837769, 1.8605706691741943, 0.8583819270133972, 1.0317699909210205, 1.9791713953018188, 1.970784068107605, 1.502771258354187, 1.2542349100112915, 1.0550950765609741, 1.1365963220596313, 1.2609230279922485, 0.8021718263626099, 1.5051189661026, 1.728963851928711, 1.2845654487609863, 1.6120938062667847, 1.6824392080307007, 1.1657017469406128, 1.532193899154663, 1.3732264041900635, 1.5059362649917603, 0.9491251111030579, 1.569008708000183, 1.4391487836837769, 2.0832276344299316, 1.7778390645980835, 0.9525631666183472, 1.1245536804199219, 1.5554277896881104, 1.3089607954025269, 1.142075777053833, 1.6430103778839111, 1.1359469890594482, 1.8727692365646362, 1.6723886728286743, 0.8456214070320129, 2.265937566757202, 1.6830984354019165, 1.6094118356704712, 0.8953531384468079, 0.9455686807632446, 1.5618298053741455, 1.7900680303573608, 1.7050912380218506, 1.1056894063949585, 1.3073350191116333, 1.4830480813980103, 1.0195027589797974, 1.3776978254318237, 1.6787444353103638, 1.3015103340148926, 0.9981910586357117, 1.0282747745513916, 1.2692574262619019, 1.5108753442764282, 1.1079834699630737, 1.1338520050048828, 1.0575764179229736, 1.6073578596115112, 1.164470911026001, 1.5303467512130737, 1.2888038158416748, 1.5700219869613647, 0.9801042675971985, 2.12646222114563, 1.4418668746948242, 1.5300556421279907, 1.8038599491119385, 1.1056339740753174, 0.7738193869590759, 1.3342663049697876, 1.7988238334655762, 0.8754059672355652, 1.5720888376235962, 1.3591194152832031, 1.4904828071594238, 1.2183208465576172, 1.408629059791565, 1.6249767541885376, 1.7602615356445312, 1.2523428201675415, 1.9469273090362549, 1.473401427268982, 1.1203542947769165, 1.4030358791351318, 1.2577643394470215, 1.6832948923110962, 1.137302041053772, 1.329734206199646, 2.231161117553711, 1.5053765773773193, 1.2001690864562988, 1.2599923610687256, 1.480346918106079, 1.4626827239990234, 1.4671550989151, 1.569480299949646, 1.1997007131576538, 1.453305959701538, 1.648934006690979, 1.2506370544433594, 1.3385632038116455, 1.4464646577835083, 1.3288546800613403, 1.6027017831802368, 1.378206729888916, 1.3534471988677979, 1.419284462928772, 1.518058180809021, 0.8924183249473572, 1.2994353771209717, 1.1934473514556885, 1.0203096866607666, 1.1896926164627075, 0.8426467776298523, 1.8704502582550049, 1.1685242652893066, 1.2836428880691528, 0.840907871723175, 0.9578842520713806, 0.9729337692260742, 1.93129563331604, 1.8438796997070312, 1.7633546590805054, 0.792247474193573, 1.1352235078811646, 0.9871677756309509, 1.1548004150390625, 1.311861515045166, 1.3541204929351807, 0.9159502983093262, 1.844523549079895, 1.1573355197906494, 0.9143328666687012, 1.456033706665039, 1.1958478689193726, 1.2542994022369385, 1.9271858930587769, 1.4978731870651245, 1.541329264640808, 1.4681848287582397, 1.170816421508789, 1.086296796798706, 1.8746044635772705, 0.8355693817138672, 2.402291774749756, 1.4263197183609009, 1.9426510334014893, 1.4020642042160034, 1.7548766136169434, 1.5866619348526, 1.5302104949951172, 1.148763656616211, 1.639296531677246, 2.0412204265594482, 1.451387643814087, 1.1540814638137817, 1.4317829608917236, 1.302343726158142, 1.4054441452026367, 1.151010513305664, 1.6867142915725708, 2.0252790451049805, 1.4264312982559204, 1.0997414588928223, 1.2578465938568115, 1.9438345432281494, 1.719030737876892, 1.050486445426941, 1.152119517326355, 1.2539467811584473, 1.059723138809204, 1.2612268924713135, 1.610241413116455, 105.376220703125, 138.844970703125, 78.7623291015625, 66.47151184082031, 38.936893463134766, 57.81634521484375, 32.46097946166992, 217.06591796875, 142.43194580078125, 293.68707275390625, 27.38525390625, 159.60406494140625, 48.74266052246094, 131.66294860839844, 143.5711669921875, 41.81658935546875, 238.8887481689453, 27.788888931274414, 37.41337203979492, 154.39344787597656, 28.420257568359375, 129.04949951171875, 167.36456298828125, 43.58649444580078, 64.79364776611328, 123.22672271728516, 25.30218505859375, 73.09536743164062, 38.580078125, 108.684814453125, 70.68177032470703, 87.79903411865234, 108.75074768066406, 49.158504486083984, 153.56207275390625, 127.93231201171875, 58.351318359375, 104.35363006591797, 20.11158561706543, 149.04270935058594, 84.7674789428711, 156.4764404296875, 183.8955841064453, 110.076171875, 143.50335693359375, 90.614013671875, 90.0267105102539, 145.24856567382812, 174.7375030517578, 36.69512939453125, 41.36480712890625, 45.631805419921875, 130.80567932128906, 46.482479095458984, 58.975257873535156, 23.161468505859375, 95.65694427490234, 120.98944091796875, 25.791250228881836, 49.1702880859375, 114.26190948486328, 199.45654296875, 185.7034912109375, 185.2147674560547, 43.71670150756836, 41.98855972290039, 102.89569091796875, 94.03558349609375, 135.76683044433594, 62.183895111083984, 102.87529754638672, 34.27370834350586, 88.65782928466797, 174.5756378173828, 30.64849853515625, 284.36962890625, 230.3084259033203, 76.99159240722656, 31.99339485168457, 29.69256591796875, 91.4451675415039, 98.604736328125, 94.09027099609375, 178.041015625, 64.82260131835938, 76.0552978515625, 129.03709411621094, 73.91128540039062, 61.50832748413086, 85.69400024414062, 58.976619720458984, 148.12158203125, 99.24505615234375, 22.725921630859375, 64.99962615966797, 168.0961456298828, 152.57693481445312, 60.643455505371094, 24.32168960571289, 75.25726318359375, 160.19662475585938, 104.35167694091797, 305.78350830078125, 94.31851196289062, 34.076019287109375, 98.5865249633789, 63.084877014160156, 151.61106872558594, 72.2602310180664, 172.83917236328125, 39.27798080444336, 94.1100082397461, 28.426204681396484, 34.31787109375, 136.93817138671875, 40.5228271484375, 51.22975158691406, 44.5067138671875, 385.5576171875, 90.1803970336914, 20.14990234375, 37.31680679321289, 21.394287109375, 91.90388488769531, 107.32503509521484, 52.019866943359375, 79.39990234375, 305.47821044921875, 309.7590026855469, 29.17498779296875, 87.37339782714844, 226.38624572753906, 147.98011779785156, 135.48934936523438, 71.2685546875, 101.32875061035156, 24.3323974609375, 207.16758728027344, 35.3524169921875, 163.1281280517578, 115.59271240234375, 38.603759765625, 31.592376708984375, 194.89456176757812, 124.91737365722656, 26.287353515625, 124.48661041259766, 87.70198822021484, 65.60511779785156, 113.74028778076172, 86.6338882446289, 155.3658447265625, 201.6142578125, 99.144775390625, 225.52001953125, 149.00770568847656, 96.95085906982422, 52.2227783203125, 61.04367446899414, 77.89425659179688, 26.74224853515625, 41.01185607910156, 69.47267150878906, 124.36038970947266, 31.0069522857666, 130.11346435546875, 147.0133056640625, 44.4224853515625, 152.4711151123047, 35.68797302246094, 50.62862014770508, 198.6833953857422, 97.58165740966797, 104.08161163330078, 28.70623779296875, 80.2689208984375, 218.1673583984375, 136.67919921875, 24.97906494140625, 169.037841796875, 207.7860565185547, 137.5960693359375, 39.17120361328125, 98.1307373046875, 147.56668090820312, 152.023193359375, 55.18459701538086, 207.07554626464844, 39.21380615234375, 142.87649536132812, 119.16925811767578, 96.00286865234375, 125.05267333984375, 158.68338012695312, 82.18956756591797, 84.95597839355469, 228.29171752929688, 65.8658218383789, 49.44851303100586, 174.17230224609375, 188.79473876953125, 90.03060150146484, 18.458740234375, 110.1083984375, 41.3214111328125, 167.551513671875, 25.083251953125, 47.0628662109375, 31.193769454956055, 206.6084747314453, 70.46917724609375, 73.77704620361328, 172.39111328125, 218.8960723876953, 75.56716918945312, 40.36127471923828, 115.83695220947266, 136.96783447265625, 135.1874237060547, 48.181209564208984, 287.60589599609375, 177.31964111328125, 41.10955810546875, 149.63568115234375, 31.30085563659668, 109.37345123291016, 171.97265625, 39.01459503173828, 207.37217712402344, 106.93868255615234, 209.24725341796875, 30.78399658203125, 114.85653686523438, 48.27779006958008, 118.9061279296875, 173.9033966064453, 78.85000610351562, 30.27032470703125, 30.368314743041992, 156.74722290039062, 199.5505828857422, 77.440185546875, 69.36901092529297, 89.83013153076172, 36.62874984741211, 31.346097946166992, 36.62868881225586, 43.95746994018555, 60.3817138671875, 41.89599609375, 31.5953369140625, 51.755252838134766, 33.58799743652344, 41.262298583984375, 34.6451416015625, 165.56893920898438, 47.49428939819336, 126.93926239013672, 145.83123779296875, 192.7364044189453, 117.70830535888672, 90.8539810180664, 41.043212890625, 151.68612670898438, 104.8554458618164, 94.1972427368164, 94.50827026367188, 228.1262664794922, 197.7509307861328, 38.66736602783203, 167.4803924560547, 127.23307037353516, 141.56060791015625, 164.81448364257812, 40.80108642578125, 94.634033203125, 180.345703125, 48.27500915527344, 60.04584884643555, 31.83270263671875, 104.6043930053711, 74.03543090820312, 112.35920715332031, 139.45758056640625, 131.3544921875, 165.88987731933594, 75.63042449951172, 89.1684341430664, 210.87319946289062, 142.4888458251953, 230.6269073486328, 157.67617797851562, 78.8125, 65.52261352539062, 167.84835815429688, 343.8204650878906, 58.371639251708984, 26.916107177734375, 104.39259338378906, 55.974945068359375, 2.7896759510040283, 3.453826904296875, 1.5667415857315063, 2.677821397781372, 2.854722738265991, 1.7467131614685059, 3.3247368335723877, 2.264777183532715, 2.048285722732544, 2.759798765182495, 1.9293564558029175, 1.750722050666809, 2.8767802715301514, 2.205137252807617, 2.8289291858673096, 1.1514005661010742, 2.5098984241485596, 3.0352938175201416, 3.3709490299224854, 1.9500837326049805, 2.0321969985961914, 1.2277708053588867, 1.6029595136642456, 1.9821946620941162, 3.5397021770477295, 1.242573857307434, 1.6723374128341675, 2.294529914855957, 1.9726303815841675, 2.454045295715332, 2.859902858734131, 1.5437579154968262, 3.3034472465515137, 2.5965945720672607, 3.2444188594818115, 2.9220402240753174, 2.5511186122894287, 2.8001129627227783, 1.0005539655685425, 3.334750175476074, 1.943215250968933, 1.7270349264144897, 3.438375234603882, 2.5444726943969727, 3.5388271808624268, 2.8202850818634033, 3.4005088806152344, 2.239598274230957, 1.8093563318252563, 2.07794451713562, 3.2421083450317383, 3.354558229446411, 2.8306431770324707, 2.124142646789551, 1.8011542558670044, 1.9686291217803955, 3.926884651184082, 2.08788800239563, 2.37304949760437, 1.620525598526001, 3.1003434658050537, 2.415055990219116, 1.88563871383667, 1.9559754133224487, 3.127514600753784, 2.7229092121124268, 3.0003247261047363, 2.180673122406006, 2.639284610748291, 2.533602237701416, 2.5787596702575684, 3.051694869995117, 3.5988805294036865, 2.9075329303741455, 3.069283962249756, 1.9552946090698242, 1.4736614227294922, 2.2483162879943848, 2.268620491027832, 1.6416786909103394, 2.105738639831543, 1.9756592512130737, 2.238703727722168, 3.917447090148926, 2.7906551361083984, 2.281111717224121, 2.5446808338165283, 2.313288927078247, 2.9904732704162598, 2.5376036167144775, 3.855226993560791, 4.017261028289795, 1.7941555976867676, 2.935157060623169, 2.6204991340637207, 2.337887763977051, 2.551363945007324, 3.4690678119659424, 3.107922315597534, 2.766909122467041, 3.3268394470214844, 1.9162911176681519, 2.664966106414795, 2.6241655349731445, 3.219252347946167, 3.27197003364563, 1.9592254161834717, 3.079449415206909, 2.6525957584381104, 1.1857956647872925, 2.337348699569702, 3.0557820796966553, 2.0469396114349365, 3.565924882888794, 1.6235442161560059, 2.458950996398926, 1.6294907331466675, 1.6151803731918335, 1.7284477949142456, 1.8931243419647217, 2.8245651721954346, 2.6186211109161377, 2.5996618270874023, 1.3215821981430054, 1.824844479560852, 1.9927493333816528, 2.31919002532959, 2.5755484104156494, 2.736875534057617, 2.6647441387176514, 2.4895355701446533, 2.4975788593292236, 2.4179611206054688, 1.3181411027908325, 3.5718626976013184, 3.622711181640625, 1.8652029037475586, 2.9621124267578125, 1.629370093345642, 2.785191774368286, 1.8356733322143555, 1.6131869554519653, 1.8528159856796265, 2.953117847442627, 3.1938164234161377, 1.9932198524475098, 2.4905765056610107, 2.238953113555908, 2.514998435974121, 2.131218910217285, 3.110178232192993, 2.614135265350342, 1.987959861755371, 3.8879289627075195, 4.159661293029785, 2.9501609802246094, 2.8982677459716797, 2.806588649749756, 2.0851755142211914, 1.734150767326355, 3.803300619125366, 2.2060117721557617, 2.274449348449707, 3.408876895904541, 2.8000547885894775, 3.084282875061035, 2.1566267013549805, 2.5453402996063232, 1.9308593273162842, 2.7899632453918457, 3.5449376106262207, 2.1688947677612305, 3.422257661819458, 2.3292016983032227, 2.743361234664917, 1.6922674179077148, 2.712815523147583, 2.891974687576294, 2.528984546661377, 2.399041175842285, 1.936564326286316, 2.3965768814086914, 1.6992368698120117, 2.363720178604126, 1.606257438659668, 2.093154191970825, 2.4611387252807617, 2.880683183670044, 2.995162010192871, 2.9872512817382812, 1.8504036664962769, 3.256586790084839, 2.269394874572754, 2.197434425354004, 2.0242607593536377, 3.1543514728546143, 2.2284786701202393, 3.391819477081299, 3.9314146041870117, 1.6206449270248413, 1.7685935497283936, 2.85483455657959, 1.7198723554611206, 2.515267848968506, 2.9264018535614014, 1.384987711906433, 2.4862871170043945, 2.8586456775665283, 3.818727970123291, 2.1672356128692627, 2.9365265369415283, 1.7311562299728394, 2.832097053527832, 2.4362804889678955, 2.6635613441467285, 2.5234439373016357, 1.9004260301589966, 1.8458449840545654, 3.5311365127563477, 2.486811399459839, 1.8688236474990845, 1.388460397720337, 2.5685319900512695, 2.362593650817871, 3.631056785583496, 2.6375396251678467, 1.3682109117507935, 2.723820447921753, 1.602766990661621, 2.1657965183258057, 2.9117279052734375, 2.060176134109497, 2.6930651664733887, 2.301549196243286, 2.9525346755981445, 1.9930497407913208, 2.2661471366882324, 2.1898930072784424, 1.782820701599121, 2.983067750930786, 2.0658464431762695, 2.9326226711273193, 1.9078987836837769, 2.5223536491394043, 1.8164417743682861, 2.3122379779815674, 2.8126790523529053, 2.192371129989624, 2.0683679580688477, 2.9136860370635986, 1.9181547164916992, 1.6410208940505981, 1.500166893005371, 2.5627222061157227, 2.964390754699707, 2.5681564807891846, 1.951252818107605, 3.2374746799468994, 4.087376594543457, 2.1081955432891846, 1.831472635269165, 1.9828828573226929, 2.160325050354004, 2.7169694900512695, 2.357973337173462, 2.8620598316192627, 3.2738330364227295, 1.6534757614135742, 3.289236068725586, 2.194303035736084, 1.7971028089523315, 2.533963203430176, 2.4699530601501465, 1.9438027143478394, 2.800258159637451, 2.000796318054199, 2.7833569049835205, 1.6734938621520996, 2.100917339324951, 1.6915887594223022, 1.5563433170318604, 2.020627498626709, 2.356358528137207, 1.3746312856674194, 3.0209782123565674, 2.7152206897735596, 1.5152883529663086, 3.7879302501678467, 2.487433433532715, 2.5765929222106934, 2.12375807762146, 1.1379576921463013, 2.021578788757324, 3.650202512741089, 1.748526930809021, 1.5503110885620117, 2.141879081726074, 3.377579927444458, 3.2717907428741455, 2.3677072525024414, 0.18206238746643066, 0.09944797307252884, 0.14383915066719055, 0.15517356991767883, 0.18572162091732025, 0.114717498421669, 0.1296224147081375, 0.2540488541126251, 0.18017825484275818, 0.12077023088932037, 0.20456178486347198, 0.23105478286743164, 0.11936291307210922, 0.16965021193027496, 0.19192688167095184, 0.12471862882375717, 0.07058954238891602, 0.15179041028022766, 0.12341853976249695, 0.14562132954597473, 0.14905251562595367, 0.23219676315784454, 0.17802180349826813, 0.1800556182861328, 0.15132750570774078, 0.15025685727596283, 0.17706584930419922, 0.12468545883893967, 0.11506666243076324, 0.1347997784614563, 0.11839818954467773, 0.15434026718139648, 0.2197999358177185, 0.18074630200862885, 0.22897948324680328, 0.13188157975673676, 0.1506495475769043, 0.1455295979976654, 0.1684824675321579, 0.11794538050889969, 0.18992866575717926, 0.17596741020679474, 0.2134046107530594, 0.10637198388576508, 0.17097388207912445, 0.17760208249092102, 0.21850267052650452, 0.22383326292037964, 0.22912852466106415, 0.1618369221687317, 0.3067988157272339, 0.19439536333084106, 0.1466013640165329, 0.20627759397029877, 0.15257859230041504, 0.11603087186813354, 0.22581036388874054, 0.17407384514808655, 0.061690643429756165, 0.1217079684138298, 0.16469331085681915, 0.17087210714817047, 0.20573383569717407, 0.12224318832159042, 0.2090826779603958, 0.15833377838134766, 0.13932274281978607, 0.11734520643949509, 0.21296870708465576, 0.1723741888999939, 0.17172475159168243, 0.19052764773368835, 0.17933566868305206, 0.1323348432779312, 0.11779352277517319, 0.13306722044944763, 0.16030253469944, 0.14026078581809998, 0.22254829108715057, 0.240909606218338, 0.18396049737930298, 0.15416225790977478, 0.07164157927036285, 0.14291107654571533, 0.20710720121860504, 0.1482461839914322, 0.16621577739715576, 0.10352364182472229, 0.193686842918396, 0.18264110386371613, 0.11588628590106964, 0.22173337638378143, 0.16810350120067596, 0.1164935827255249, 0.2043156623840332, 0.13748973608016968, 0.1354314684867859, 0.20831482112407684, 0.22254061698913574, 0.19055293500423431, 0.13904023170471191, 0.14989520609378815, 0.11219363659620285, 0.191170796751976, 0.15399207174777985, 0.17403869330883026, 0.17759013175964355, 0.2254013568162918, 0.1538628488779068, 0.15994909405708313, 0.0915927067399025, 0.10275784879922867, 0.13957370817661285, 0.21019874513149261, 0.2223414182662964, 0.22469346225261688, 0.1273745447397232, 0.1919190138578415, 0.19678764045238495, 0.19884902238845825, 0.2014431655406952, 0.12173152714967728, 0.13981521129608154, 0.18721050024032593, 0.15349623560905457, 0.2075999528169632, 0.14448773860931396, 0.24585914611816406, 0.21971188485622406, 0.17716261744499207, 0.15815997123718262, 0.1297035962343216, 0.18035711348056793, 0.23224997520446777, 0.16863620281219482, 0.18079540133476257, 0.09895775467157364, 0.2067655324935913, 0.16026897728443146, 0.1676287204027176, 0.2384730875492096, 0.20377925038337708, 0.20747609436511993, 0.1336810141801834, 0.128049835562706, 0.15757855772972107, 0.16687346994876862, 0.2250586599111557, 0.180821493268013, 0.178140327334404, 0.19129718840122223, 0.16334930062294006, 0.1434071958065033, 0.19827334582805634, 0.21473653614521027, 0.15166082978248596, 0.23302923142910004, 0.2514496445655823, 0.170308455824852, 0.19534064829349518, 0.21418526768684387, 0.14950911700725555, 0.22636422514915466, 0.163328617811203, 0.18796338140964508, 0.16844803094863892, 0.2082882672548294, 0.22974427044391632, 0.17796754837036133, 0.10412843525409698, 0.17122216522693634, 0.14389543235301971, 0.1327642947435379, 0.18687193095684052, 0.17178402841091156, 0.17256037890911102, 0.1812954992055893, 0.1863642781972885, 0.1519988626241684, 0.2039596140384674, 0.17938151955604553, 0.19801200926303864, 0.16191436350345612, 0.21411903202533722, 0.2084113210439682, 0.1898398995399475, 0.20688922703266144, 0.13572703301906586, 0.1729211062192917, 0.16197650134563446, 0.14558057487010956, 0.20452983677387238, 0.11997135728597641, 0.18370315432548523, 0.17687049508094788, 0.12101750820875168, 0.1472228765487671, 0.18357165157794952, 0.16629429161548615, 0.1436738222837448, 0.2029208391904831, 0.13621190190315247, 0.10304124653339386, 0.19456340372562408, 0.16114987432956696, 0.20448105037212372, 0.10443102568387985, 0.21326598525047302, 0.17646293342113495, 0.18299934267997742, 0.16454507410526276, 0.15950939059257507, 0.1743546575307846, 0.20534104108810425, 0.14350205659866333, 0.1952010691165924, 0.1849031001329422, 0.1997348815202713, 0.17500975728034973, 0.16699372231960297, 0.16061551868915558, 0.1512497514486313, 0.19528689980506897, 0.26389411091804504, 0.14962661266326904, 0.12257079035043716, 0.1502506583929062, 0.21222618222236633, 0.11854329705238342, 0.18134118616580963, 0.1426936686038971, 0.18010301887989044, 0.19573695957660675, 0.12421149760484695, 0.20330846309661865, 0.20351897180080414, 0.14905889332294464, 0.2032218724489212, 0.2909020185470581, 0.23947890102863312, 0.16441825032234192, 0.17271991074085236, 0.15331874787807465, 0.17162345349788666, 0.183648943901062, 0.21011047065258026, 0.21839554607868195, 0.1535058468580246, 0.17833518981933594, 0.21489852666854858, 0.1693844348192215, 0.17796626687049866, 0.10098787397146225, 0.15729346871376038, 0.13087664544582367, 0.15769357979297638, 0.13907186686992645, 0.18682876229286194, 0.17923840880393982, 0.10302868485450745, 0.13729077577590942, 0.1934153139591217, 0.17888712882995605, 0.19079625606536865, 0.14389552175998688, 0.21111811697483063, 0.15542756021022797, 0.1627211570739746, 0.14024466276168823, 0.13125228881835938, 0.17457404732704163, 0.2030685991048813, 0.18130441009998322, 0.18353445827960968, 0.17004874348640442, 0.22342704236507416, 0.15048007667064667, 0.18456915020942688, 0.190973162651062, 0.1923997849225998, 0.22003477811813354, 0.20251904428005219, 0.16602592170238495, 0.19353382289409637, 0.1277550756931305, 0.17279911041259766, 0.10310592502355576, 0.14604870975017548, 0.19072583317756653, 0.19537730515003204, 0.1946314573287964, 0.1710251271724701, 0.1412542313337326, 0.154861718416214, 0.14488546550273895, 0.19919443130493164, 0.19164562225341797, 0.16547523438930511, 0.13585036993026733, 0.19506259262561798, 1.3709176778793335, 1.5992624759674072, 1.486444115638733, 1.001241683959961, 1.5403350591659546, 1.0025029182434082, 0.8427778482437134, 1.6307852268218994, 1.434725284576416, 1.787723183631897, 0.9419232606887817, 1.6241950988769531, 1.8466393947601318, 1.5843628644943237, 1.4814579486846924, 1.5084326267242432, 1.1312123537063599, 2.0541539192199707, 2.4038727283477783, 1.4020309448242188, 2.065215826034546, 1.2471530437469482, 1.449578881263733, 1.9178582429885864, 0.955470085144043, 1.4551446437835693, 1.2387495040893555, 1.58541738986969, 1.601776123046875, 0.8105142712593079, 1.8719784021377563, 0.5268850326538086, 1.2396970987319946, 1.9551359415054321, 1.4122883081436157, 1.3308700323104858, 1.0751067399978638, 1.3079458475112915, 1.0806047916412354, 1.3370071649551392, 2.1306991577148438, 1.9320696592330933, 1.1816469430923462, 2.112976551055908, 0.9539481401443481, 0.899332582950592, 1.7483183145523071, 1.9725966453552246, 1.395377516746521, 1.9702928066253662, 1.085080862045288, 0.9988508224487305, 1.5334631204605103, 1.6344317197799683, 1.7130944728851318, 1.4917795658111572, 1.0853115320205688, 1.324172019958496, 1.4624565839767456, 2.23478102684021, 1.4182324409484863, 1.458463430404663, 1.572918176651001, 1.1844727993011475, 1.1801817417144775, 1.6168670654296875, 1.6851389408111572, 1.664387583732605, 2.323535203933716, 1.083220362663269, 1.7172335386276245, 1.5536489486694336, 1.8237932920455933, 1.9457454681396484, 1.4247896671295166, 1.3691364526748657, 1.3707650899887085, 1.9671756029129028, 0.9554389119148254, 1.4085079431533813, 1.3867144584655762, 1.4910175800323486, 1.923462152481079, 1.8731075525283813, 1.7233784198760986, 1.7255382537841797, 1.8899154663085938, 1.2895243167877197, 1.647621750831604, 1.1473749876022339, 1.9051432609558105, 1.7655893564224243, 1.0372428894042969, 1.451973795890808, 0.7148362398147583, 1.6709696054458618, 2.1097187995910645, 0.7057501077651978, 1.238757610321045, 1.2243627309799194, 1.4296196699142456, 0.7967134714126587, 1.0355072021484375, 0.8995965123176575, 2.0276849269866943, 1.1355383396148682, 0.8590238690376282, 1.163864254951477, 1.2856948375701904, 0.9292117357254028, 0.9860137104988098, 1.124751091003418, 1.136784315109253, 1.1561455726623535, 1.8412319421768188, 1.327557921409607, 1.1765416860580444, 1.9851690530776978, 1.406171441078186, 0.9590380787849426, 1.5803234577178955, 0.8285171985626221, 1.1984162330627441, 2.476954460144043, 1.6623238325119019, 2.333374261856079, 1.1890029907226562, 1.8448055982589722, 0.8859084248542786, 1.667589545249939, 1.604767084121704, 2.025611162185669, 0.8551026582717896, 2.304276466369629, 1.1847329139709473, 1.5157816410064697, 2.036055326461792, 1.2237157821655273, 1.9168611764907837, 1.9865658283233643, 1.378939151763916, 0.8035532236099243, 1.1497008800506592, 0.9795529246330261, 0.8294761180877686, 1.5159307718276978, 1.1683052778244019, 2.127488851547241, 1.8465465307235718, 2.1250479221343994, 0.7013571858406067, 1.0065068006515503, 0.8560954332351685, 1.1766215562820435, 1.2466204166412354, 1.8810503482818604, 1.281015157699585, 1.8831173181533813, 1.1320955753326416, 1.3171731233596802, 1.3783947229385376, 0.9900838136672974, 1.7630239725112915, 1.6011499166488647, 0.8945603966712952, 0.7314193844795227, 1.1068997383117676, 1.159706950187683, 1.904268741607666, 0.8939836621284485, 1.155203104019165, 0.8299996256828308, 1.5596932172775269, 1.192605972290039, 1.4141193628311157, 1.869341492652893, 1.5664364099502563, 1.481146216392517, 1.831618309020996, 1.1551836729049683, 1.1190842390060425, 1.3594597578048706, 1.5391956567764282, 1.7816250324249268, 1.6012879610061646, 1.5976154804229736, 1.2003861665725708, 1.4645159244537354, 1.547188401222229, 1.2586917877197266, 1.3474520444869995, 1.6941713094711304, 1.6092873811721802, 1.763128638267517, 1.29742431640625, 1.1060640811920166, 1.3782503604888916, 1.7637722492218018, 1.0498452186584473, 1.4858171939849854, 2.0243241786956787, 1.7672637701034546, 0.9440032839775085, 1.198976755142212, 0.9311752319335938, 1.6044889688491821, 1.5928713083267212, 1.5365869998931885, 1.6024023294448853, 1.5321578979492188, 1.3952829837799072, 1.2491321563720703, 1.7289186716079712, 1.044959545135498, 1.1497802734375, 1.3545483350753784, 1.9657607078552246, 1.375848412513733, 2.214021921157837, 1.2843899726867676, 1.6080940961837769, 1.5899423360824585, 1.039189100265503, 1.1434803009033203, 1.1483715772628784, 1.4055753946304321, 1.5076398849487305, 1.6193228960037231, 1.1644400358200073, 1.8239824771881104, 1.3243615627288818, 1.5235201120376587, 1.6076573133468628, 1.5923982858657837, 2.0966527462005615, 1.6449095010757446, 1.4443258047103882, 1.261322021484375, 1.5042587518692017, 1.4258896112442017, 3.0208375453948975, 1.0906720161437988, 1.5810930728912354, 1.7381752729415894, 2.0598020553588867, 1.3901498317718506, 1.226689100265503, 1.508498191833496, 1.5840181112289429, 2.011361837387085, 2.0105037689208984, 1.3748177289962769, 1.8336882591247559, 1.4059832096099854, 2.0538840293884277, 0.8508636355400085, 1.2503386735916138, 2.0976691246032715, 1.1116321086883545, 0.9563886523246765, 1.0176491737365723, 1.2694052457809448, 1.493859887123108, 1.6873773336410522, 1.9935698509216309, 1.791735291481018, 1.092818260192871, 1.5873955488204956, 1.708984613418579, 1.6128442287445068, 1.0979152917861938, 1.1304007768630981, 1.131575584411621, 1.8188167810440063, 1.2184438705444336, 2.1605050563812256, 1.14384925365448, 1.4524017572402954, 1.957827091217041, 1.8847843408584595, 1.9592170715332031, 1.6257299184799194, 2.446424722671509, 1.1832659244537354, 0.9608588218688965, 1.451973557472229, 1.355767846107483, 1.266371488571167, 2.1555135250091553, 1.2582290172576904, 1.1171412467956543, 2.004410743713379, 1.1650879383087158, 1.5448824167251587, 1.9817017316818237, 1.099552035331726, 1.2683582305908203, 1.292056679725647, 1.1146395206451416, 1.3574923276901245, 178.04124450683594, 207.7373046875, 37.02347946166992, 128.38388061523438, 121.7244873046875, 30.73114013671875, 153.90414428710938, 37.88565444946289, 99.21404266357422, 106.00312042236328, 37.34074020385742, 32.15008544921875, 52.877197265625, 43.72388458251953, 32.23529052734375, 30.27484130859375, 68.7771987915039, 63.48577880859375, 52.815242767333984, 183.1419677734375, 44.856014251708984, 85.74690246582031, 26.59326171875, 72.40985107421875, 63.55139923095703, 88.3012466430664, 86.427001953125, 82.805419921875, 40.86549377441406, 41.81341552734375, 121.74679565429688, 191.0299835205078, 170.78184509277344, 239.5644073486328, 151.75408935546875, 38.083396911621094, 106.49405670166016, 122.29339599609375, 122.664794921875, 35.9172477722168, 136.39474487304688, 58.72182846069336, 61.32098388671875, 88.1917724609375, 105.96209716796875, 23.398807525634766, 114.79622650146484, 42.26702880859375, 40.18659591674805, 191.419921875, 46.239891052246094, 189.47300720214844, 174.91514587402344, 40.27008056640625, 75.02288818359375, 99.01911926269531, 73.75883483886719, 29.76944351196289, 239.99462890625, 93.48392486572266, 21.7188720703125, 101.6903076171875, 93.68240356445312, 76.7491455078125, 98.64884185791016, 85.2308349609375, 154.6857147216797, 82.62825012207031, 235.9890899658203, 85.02104949951172, 39.65091323852539, 167.02317810058594, 102.33477020263672, 101.7946548461914, 123.08258819580078, 60.170989990234375, 114.37017059326172, 181.32054138183594, 189.1175079345703, 36.10410690307617, 72.10580444335938, 166.48744201660156, 123.67626953125, 149.71766662597656, 46.129940032958984, 29.39105224609375, 26.1376953125, 193.9337921142578, 113.77497863769531, 176.0558624267578, 248.6352996826172, 60.994754791259766, 87.21060180664062, 25.51373291015625, 31.5968017578125, 24.98101806640625, 71.71185302734375, 28.28570556640625, 129.03700256347656, 58.124481201171875, 153.70762634277344, 76.92118072509766, 43.275390625, 38.828792572021484, 121.1913833618164, 190.1078643798828, 104.65757751464844, 136.89810180664062, 149.68753051757812, 56.07611083984375, 121.98109436035156, 217.2935333251953, 177.35089111328125, 61.97053527832031, 53.905120849609375, 107.84111022949219, 56.4547004699707, 130.0487823486328, 226.57080078125, 37.17177963256836, 272.3590087890625, 202.82835388183594, 152.04666137695312, 27.0380859375, 112.1912841796875, 76.6828384399414, 27.274139404296875, 78.24254608154297, 160.76626586914062, 124.53311920166016, 67.29148864746094, 82.2751235961914, 45.65382766723633, 105.47246551513672, 97.7069091796875, 225.8169708251953, 45.765926361083984, 61.65156173706055, 118.77239990234375, 100.96892547607422, 98.617919921875, 153.990478515625, 49.8614501953125, 22.5172119140625, 56.06167984008789, 104.47186279296875, 126.12979888916016, 198.46023559570312, 110.53282928466797, 201.6126708984375, 75.49822998046875, 130.02618408203125, 57.37525177001953, 177.5399169921875, 151.72454833984375, 70.82540893554688, 81.09078216552734, 37.733154296875, 101.3881607055664, 187.9209747314453, 38.98737335205078, 48.891845703125, 88.03314208984375, 84.49896240234375, 37.62619400024414, 35.86663818359375, 49.47227096557617, 81.1927490234375, 111.8793716430664, 60.17499923706055, 151.25390625, 57.620418548583984, 21.201688766479492, 132.84043884277344, 180.9391632080078, 83.28564453125, 154.13417053222656, 151.43959045410156, 26.967987060546875, 134.23651123046875, 125.6598892211914, 31.22884178161621, 87.70068359375, 33.5631103515625, 51.89715576171875, 129.79637145996094, 192.36253356933594, 65.71698760986328, 210.87657165527344, 140.65625, 95.9657211303711, 26.6796875, 50.35197067260742, 35.101016998291016, 38.906097412109375, 30.95062255859375, 193.57296752929688, 139.48367309570312, 192.38577270507812, 75.0107421875, 52.712528228759766, 216.45703125, 39.835941314697266, 118.1454849243164, 145.37600708007812, 83.48120880126953, 192.82763671875, 82.36908721923828, 151.85845947265625, 90.53094482421875, 110.17352294921875, 80.06311798095703, 40.5128059387207, 21.385087966918945, 69.1786880493164, 179.063232421875, 111.86492919921875, 82.11537170410156, 26.829008102416992, 47.61798095703125, 21.52911376953125, 51.77651596069336, 27.87070655822754, 95.21658325195312, 93.94835662841797, 29.1998291015625, 170.775390625, 146.90283203125, 142.96847534179688, 41.636478424072266, 163.7998046875, 58.10486602783203, 23.851957321166992, 87.43712615966797, 67.54296875, 92.44769287109375, 35.61376953125, 108.37682342529297, 63.48983383178711, 45.039466857910156, 45.1851806640625, 106.90164184570312, 152.05628967285156, 158.994873046875, 173.6727294921875, 44.91627883911133, 147.57012939453125, 103.54061889648438, 179.764404296875, 105.0107421875, 98.18727111816406, 104.75835418701172, 169.38058471679688, 50.163211822509766, 75.1883544921875, 77.65029907226562, 31.777650833129883, 101.23148345947266, 184.0720977783203, 94.892578125, 195.2674560546875, 22.11138916015625, 199.7332763671875, 83.8316879272461, 54.56653594970703, 63.001708984375, 200.28733825683594, 101.31878662109375, 62.541664123535156, 153.2877655029297, 49.396141052246094, 87.40538787841797, 65.08755493164062, 79.39456176757812, 70.53143310546875, 119.474365234375, 21.420333862304688, 166.20565795898438, 134.81353759765625, 53.58733367919922, 197.689453125, 87.75311279296875, 206.53781127929688, 36.191253662109375, 143.87728881835938, 74.35121154785156, 90.80511474609375, 135.49972534179688, 101.91222381591797, 116.15141296386719, 139.69134521484375, 96.98023986816406, 42.664852142333984, 33.26910400390625, 135.5167236328125, 206.33616638183594, 66.74148559570312, 144.7576904296875, 237.23583984375, 108.89263153076172, 2.0608503818511963, 2.39739990234375, 2.6834352016448975, 1.5900200605392456, 3.999337911605835, 1.5310355424880981, 3.3730058670043945, 3.08376407623291, 2.873037099838257, 1.9422848224639893, 3.275904417037964, 1.7584317922592163, 1.9696998596191406, 4.156383991241455, 1.8995428085327148, 3.0386688709259033, 2.768864631652832, 2.7658910751342773, 2.7300827503204346, 2.868252754211426, 3.3413383960723877, 2.766697645187378, 2.4657533168792725, 3.1029083728790283, 1.6953362226486206, 3.0510056018829346, 3.2565014362335205, 2.6131200790405273, 2.388381004333496, 2.547978401184082, 1.5580434799194336, 3.126116991043091, 1.6217565536499023, 2.2826085090637207, 2.0103254318237305, 3.3884379863739014, 1.5515564680099487, 3.336541175842285, 3.602543830871582, 2.997241258621216, 2.7131640911102295, 1.9171905517578125, 1.5511940717697144, 2.007016181945801, 2.696971893310547, 3.1524980068206787, 2.0873749256134033, 3.0783159732818604, 2.3965535163879395, 1.6675790548324585, 2.156816244125366, 2.2711997032165527, 1.4107284545898438, 1.0796631574630737, 3.2592570781707764, 1.065557599067688, 2.850255012512207, 2.887509346008301, 1.820271611213684, 2.873683214187622, 2.6932098865509033, 3.1800737380981445, 2.232211112976074, 1.5944552421569824, 1.9235793352127075, 1.8422396183013916, 3.57590389251709, 1.562714695930481, 2.1211743354797363, 2.255751371383667, 3.5477635860443115, 2.297990560531616, 2.312832832336426, 2.6281938552856445, 1.432519555091858, 2.457839012145996, 2.4004967212677, 2.8622210025787354, 3.088104248046875, 2.4902219772338867, 3.017843008041382, 1.9188299179077148, 3.0977935791015625, 2.4233298301696777, 4.224078178405762, 2.4119653701782227, 2.3772168159484863, 2.209728240966797, 2.875386953353882, 1.508390188217163, 3.140451669692993, 1.7077986001968384, 2.5681657791137695, 1.9318584203720093, 1.8300906419754028, 1.7794218063354492, 2.2267158031463623, 2.3816123008728027, 2.271977424621582, 3.3939123153686523, 2.8535802364349365, 2.6337692737579346, 2.3487768173217773, 2.9861364364624023, 1.910073161125183, 2.962864875793457, 2.08510684967041, 2.071460008621216, 2.5411081314086914, 2.4246912002563477, 2.3422317504882812, 3.0424931049346924, 2.757216215133667, 2.0570640563964844, 3.0085880756378174, 1.8945722579956055, 2.4281816482543945, 2.587918996810913, 1.6773710250854492, 1.7309637069702148, 3.005194902420044, 2.977717638015747, 3.786074638366699, 2.334338426589966, 2.925084114074707, 2.6373419761657715, 1.9826781749725342, 2.1757047176361084, 2.396794557571411, 1.9988863468170166, 2.9466915130615234, 2.535226583480835, 2.415306329727173, 1.8238248825073242, 1.0634195804595947, 3.366516590118408, 1.7080819606781006, 1.6059867143630981, 2.7234904766082764, 1.2689383029937744, 2.232654571533203, 1.6351937055587769, 1.3516833782196045, 1.3688057661056519, 1.7912675142288208, 2.0779876708984375, 2.140852928161621, 1.854456901550293, 3.1489834785461426, 2.515110969543457, 2.257622718811035, 1.6881111860275269, 1.7627822160720825, 1.6768213510513306, 2.9332988262176514, 2.1445531845092773, 3.4049251079559326, 2.1075220108032227, 2.0085465908050537, 2.6963112354278564, 2.1408300399780273, 1.9939051866531372, 1.8478890657424927, 2.9914162158966064, 2.326857566833496, 2.362621545791626, 2.1168413162231445, 2.426417112350464, 1.4668673276901245, 2.2898550033569336, 2.1854491233825684, 1.7050179243087769, 2.3304948806762695, 1.4238004684448242, 2.712826728820801, 2.7392022609710693, 1.1360347270965576, 1.7708483934402466, 2.4216554164886475, 2.9732866287231445, 2.4441137313842773, 3.220921516418457, 1.5990796089172363, 3.1138317584991455, 2.77262020111084, 1.797286033630371, 3.0758469104766846, 2.994476318359375, 2.382267951965332, 2.3412463665008545, 2.7982139587402344, 1.707797646522522, 2.282703399658203, 2.214434862136841, 2.1166107654571533, 2.491489887237549, 3.579089641571045, 3.1980273723602295, 2.3955602645874023, 3.5377116203308105, 3.142897844314575, 2.575671672821045, 2.760695457458496, 3.093024492263794, 1.820984959602356, 2.44547176361084, 2.9562466144561768, 1.6358004808425903, 2.890570640563965, 1.7897491455078125, 2.63388729095459, 2.088886022567749, 1.6409406661987305, 1.2704426050186157, 1.5907562971115112, 2.9348080158233643, 1.9444993734359741, 2.4545419216156006, 1.9645414352416992, 2.570087194442749, 1.495326042175293, 2.4836761951446533, 2.696154832839966, 3.059019088745117, 2.5593061447143555, 3.9080235958099365, 2.933220863342285, 2.8956658840179443, 1.8463523387908936, 3.0194756984710693, 1.9294480085372925, 3.187225818634033, 1.3646764755249023, 2.2219784259796143, 1.9573986530303955, 1.8681527376174927, 2.291166067123413, 2.0097150802612305, 2.083743095397949, 1.2903234958648682, 2.551767110824585, 3.1195499897003174, 1.475624918937683, 2.610071897506714, 2.3988423347473145, 1.5698537826538086, 3.0921990871429443, 1.5254056453704834, 1.2977361679077148, 1.67893648147583, 2.6386537551879883, 1.8375005722045898, 2.60673451423645, 1.4794888496398926, 2.2953577041625977, 2.8193578720092773, 3.517566442489624, 1.3121671676635742, 1.161468744277954, 2.1987154483795166, 2.2727158069610596, 2.793872117996216, 2.9379208087921143, 2.7085866928100586, 1.6018799543380737, 1.6711055040359497, 3.7440197467803955, 2.8173186779022217, 2.0809173583984375, 2.0431206226348877, 1.6143903732299805, 2.4354519844055176, 1.5231492519378662, 3.2837798595428467, 1.916524052619934, 2.1663506031036377, 1.6051106452941895, 1.8848323822021484, 1.3083416223526, 2.971757173538208, 2.318596839904785, 1.8115148544311523, 2.619128942489624, 2.5363001823425293, 1.8278342485427856, 1.642897605895996, 1.5241941213607788, 1.513977289199829, 3.4842586517333984, 3.5793004035949707, 3.1741271018981934, 3.037125825881958, 2.3179636001586914, 2.462405204772949, 2.10360050201416, 2.9451546669006348, 2.539118766784668, 4.295825004577637, 2.156895637512207, 1.6170017719268799, 0.20942234992980957, 0.24453537166118622, 0.1330285221338272, 0.14393605291843414, 0.16724875569343567, 0.27994638681411743, 0.212112158536911, 0.15191791951656342, 0.19195720553398132, 0.17072707414627075, 0.12345129996538162, 0.17712439596652985, 0.13675165176391602, 0.18001537024974823, 0.1363527625799179, 0.20029456913471222, 0.17104332149028778, 0.17851601541042328, 0.1487296223640442, 0.2260839343070984, 0.1470409482717514, 0.21376319229602814, 0.24330340325832367, 0.20051391422748566, 0.21812346577644348, 0.18502306938171387, 0.14201900362968445, 0.14879903197288513, 0.16497838497161865, 0.17896774411201477, 0.23123759031295776, 0.16064412891864777, 0.1834111213684082, 0.17943088710308075, 0.16639412939548492, 0.19417035579681396, 0.23615117371082306, 0.13442127406597137, 0.1946648806333542, 0.16208042204380035, 0.12341022491455078, 0.17463786900043488, 0.14408883452415466, 0.15448255836963654, 0.1113968938589096, 0.15442967414855957, 0.1544177532196045, 0.148842915892601, 0.16171059012413025, 0.13344022631645203, 0.19479826092720032, 0.1434004306793213, 0.26197853684425354, 0.23187685012817383, 0.20577096939086914, 0.2115475982427597, 0.1391562819480896, 0.15943339467048645, 0.16593091189861298, 0.1705750823020935, 0.12535081803798676, 0.15858782827854156, 0.23230677843093872, 0.24078628420829773, 0.18914203345775604, 0.1638881415128708, 0.19171656668186188, 0.10938294976949692, 0.19447088241577148, 0.2046411633491516, 0.11322049796581268, 0.15746904909610748, 0.2470165640115738, 0.14288561046123505, 0.18054601550102234, 0.24199478328227997, 0.17420123517513275, 0.1743907481431961, 0.16600079834461212, 0.11404792219400406, 0.19610445201396942, 0.2561923861503601, 0.17326964437961578, 0.24180690944194794, 0.2174234688282013, 0.14390024542808533, 0.18824946880340576, 0.2495972067117691, 0.16546563804149628, 0.18064017593860626, 0.22255927324295044, 0.1952570527791977, 0.18774940073490143, 0.12877941131591797, 0.20394940674304962, 0.1552792340517044, 0.25851866602897644, 0.22047945857048035, 0.15942533314228058, 0.15127068758010864, 0.20678633451461792, 0.1503148376941681, 0.12867391109466553, 0.1413232982158661, 0.08514991402626038, 0.18166808784008026, 0.15054908394813538, 0.17240925133228302, 0.22318385541439056, 0.16796128451824188, 0.1903569996356964, 0.11768588423728943, 0.11068760603666306, 0.1456596851348877, 0.20172667503356934, 0.1878831833600998, 0.1929503232240677, 0.16222047805786133, 0.1254671961069107, 0.18714335560798645, 0.14963777363300323, 0.1812630295753479, 0.13724057376384735, 0.2321081906557083, 0.19477517902851105, 0.17280526459217072, 0.15785573422908783, 0.22057443857192993, 0.18015845119953156, 0.15406924486160278, 0.17007717490196228, 0.16267628967761993, 0.17185524106025696, 0.14046941697597504, 0.11185937374830246, 0.17612199485301971, 0.15656255185604095, 0.22678343951702118, 0.2069358080625534, 0.20651333034038544, 0.16492436826229095, 0.153066024184227, 0.14313171803951263, 0.1534833461046219, 0.21472381055355072, 0.17532281577587128, 0.2117944359779358, 0.11349975317716599, 0.18332195281982422, 0.1697547882795334, 0.15172028541564941, 0.22825568914413452, 0.1685832440853119, 0.250544011592865, 0.14178241789340973, 0.13813714683055878, 0.10681284964084625, 0.16793963313102722, 0.13541269302368164, 0.15482540428638458, 0.15428458154201508, 0.25363463163375854, 0.203586608171463, 0.21535205841064453, 0.11754468828439713, 0.14768347144126892, 0.13081996142864227, 0.2585721015930176, 0.19471342861652374, 0.1217823401093483, 0.21050876379013062, 0.23343804478645325, 0.21238166093826294, 0.17517390847206116, 0.21541985869407654, 0.17791962623596191, 0.1685471087694168, 0.24855470657348633, 0.18486744165420532, 0.16708123683929443, 0.2266278862953186, 0.12556982040405273, 0.2006998360157013, 0.18055076897144318, 0.17566967010498047, 0.21047861874103546, 0.17509086430072784, 0.20594671368598938, 0.21723639965057373, 0.131072998046875, 0.14552296698093414, 0.21083515882492065, 0.15118159353733063, 0.1693732738494873, 0.12366676330566406, 0.12420882284641266, 0.17384250462055206, 0.20335358381271362, 0.18680205941200256, 0.1679237335920334, 0.1469544917345047, 0.17401841282844543, 0.14118553698062897, 0.19583602249622345, 0.247150257229805, 0.1276693344116211, 0.1198078989982605, 0.1822877824306488, 0.14706897735595703, 0.16691012680530548, 0.11317700147628784, 0.2620694935321808, 0.1826859563589096, 0.15787498652935028, 0.14222604036331177, 0.15764732658863068, 0.21326923370361328, 0.15532881021499634, 0.19212821125984192, 0.12586236000061035, 0.11833804845809937, 0.17339026927947998, 0.21284587681293488, 0.10823468863964081, 0.12281578779220581, 0.14544500410556793, 0.22928380966186523, 0.17745688557624817, 0.2096177637577057, 0.13294009864330292, 0.13359999656677246, 0.09461920708417892, 0.20850984752178192, 0.17011407017707825, 0.17859488725662231, 0.17174574732780457, 0.18326857686042786, 0.1803150475025177, 0.1664029061794281, 0.17463739216327667, 0.21123000979423523, 0.16454005241394043, 0.24385638535022736, 0.18032169342041016, 0.14312003552913666, 0.19859248399734497, 0.2047109603881836, 0.11480654776096344, 0.1307963877916336, 0.12349959462881088, 0.1443490982055664, 0.16775116324424744, 0.13269561529159546, 0.18883270025253296, 0.2043706476688385, 0.2154558151960373, 0.23397159576416016, 0.09801993519067764, 0.12115446478128433, 0.09714090079069138, 0.19338786602020264, 0.1529301553964615, 0.1681661158800125, 0.1457129418849945, 0.16912434995174408, 0.09712697565555573, 0.1295834630727768, 0.1619727611541748, 0.14802545309066772, 0.17091065645217896, 0.17444728314876556, 0.18995511531829834, 0.13442742824554443, 0.17949335277080536, 0.14078132808208466, 0.13265542685985565, 0.1525282859802246, 0.16224412620067596, 0.19114354252815247, 0.16281844675540924, 0.14772717654705048, 0.18355350196361542, 0.13954515755176544, 0.15926289558410645, 0.14959320425987244, 0.16851969063282013, 0.14961804449558258, 0.16786274313926697, 0.16520370543003082, 0.20967629551887512, 0.15698248147964478, 0.15569822490215302, 0.16606852412223816, 0.16879132390022278, 0.23055928945541382, 0.17611457407474518, 0.21307162940502167, 0.24562446773052216, 0.19384589791297913, 0.20109322667121887, 1.844498872756958, 1.7319676876068115, 2.1609549522399902, 1.8624056577682495, 1.773510217666626, 1.0249104499816895, 1.3031688928604126, 1.2539528608322144, 1.1431221961975098, 1.6950756311416626, 1.4927473068237305, 1.5854614973068237, 1.1813195943832397, 0.7033498883247375, 1.9006136655807495, 1.4533846378326416, 1.8085068464279175, 1.5572608709335327, 0.9741767048835754, 1.299210786819458, 1.2931411266326904, 1.7542967796325684, 0.9135448932647705, 1.728441834449768, 1.5411748886108398, 1.2195086479187012, 1.621659755706787, 1.5801273584365845, 1.1497052907943726, 2.5632054805755615, 1.0513969659805298, 1.4015792608261108, 1.1531541347503662, 2.2748873233795166, 1.5775254964828491, 1.2350330352783203, 1.4455887079238892, 1.4829872846603394, 1.27787184715271, 1.0083132982254028, 1.7326736450195312, 2.121047258377075, 1.733895182609558, 1.6457372903823853, 1.2029584646224976, 1.2535655498504639, 1.1118794679641724, 1.9151769876480103, 1.967085838317871, 1.8456369638442993, 1.0645767450332642, 1.3179996013641357, 0.6819199919700623, 1.4974758625030518, 2.0067625045776367, 1.5968761444091797, 2.1651387214660645, 0.9756997227668762, 1.5963480472564697, 1.9297596216201782, 1.6292901039123535, 1.7458550930023193, 1.9836657047271729, 1.6471978425979614, 0.9257592558860779, 2.4178106784820557, 1.5529356002807617, 2.1314239501953125, 1.1883376836776733, 1.8414262533187866, 1.076827883720398, 1.8093713521957397, 0.8337066173553467, 1.1732816696166992, 1.9542230367660522, 1.6169524192810059, 1.4366286993026733, 1.105358600616455, 1.3699150085449219, 1.8469088077545166, 1.9512923955917358, 1.9156734943389893, 1.5027581453323364, 0.8592411875724792, 2.1853766441345215, 1.7747368812561035, 0.909807026386261, 1.860411524772644, 1.4437936544418335, 1.623739242553711, 1.3432978391647339, 1.102358341217041, 1.2368613481521606, 2.0917272567749023, 1.2857223749160767, 1.6034178733825684, 1.0681288242340088, 1.189849853515625, 1.3056260347366333, 0.7957665920257568, 1.3348053693771362, 1.3094297647476196, 1.91211998462677, 1.3837954998016357, 1.9461122751235962, 1.567813515663147, 1.706583857536316, 1.4189335107803345, 1.1224007606506348, 1.4203100204467773, 1.7723286151885986, 1.1353437900543213, 0.7968463897705078, 1.9717592000961304, 0.9401753544807434, 2.151890754699707, 1.9666520357131958, 1.6332305669784546, 1.311029076576233, 2.8940343856811523, 1.1362007856369019, 1.779366135597229, 2.585954427719116, 0.9251888990402222, 1.7582021951675415, 1.793312668800354, 1.5269603729248047, 1.2942477464675903, 1.1736634969711304, 1.701180100440979, 1.1029757261276245, 1.7561334371566772, 1.995955467224121, 1.5800803899765015, 0.7438748478889465, 1.4854077100753784, 0.8341334462165833, 1.972747802734375, 1.444844126701355, 0.9710873365402222, 1.4765093326568604, 1.6461730003356934, 1.2951469421386719, 1.6010286808013916, 1.7309309244155884, 0.8782289624214172, 0.8348923921585083, 1.4067611694335938, 1.3497676849365234, 1.0802894830703735, 1.145212173461914, 1.4950361251831055, 2.129058837890625, 1.1852307319641113, 1.6292451620101929, 1.8567320108413696, 1.4973722696304321, 1.7972910404205322, 1.4540483951568604, 1.3409769535064697, 1.485539197921753, 1.837585687637329, 1.8456358909606934, 1.4789522886276245, 0.6596187949180603, 1.0882010459899902, 1.6190065145492554, 1.3714643716812134, 1.7506393194198608, 1.2108008861541748, 1.7625517845153809, 1.6770986318588257, 1.0503525733947754, 1.3350207805633545, 1.7922842502593994, 1.2493224143981934, 1.7372573614120483, 1.1554259061813354, 1.4348899126052856, 0.8852702379226685, 1.7336279153823853, 0.8899425864219666, 1.7598812580108643, 1.3419468402862549, 1.0605876445770264, 1.6183022260665894, 1.9677317142486572, 1.3721107244491577, 1.6191115379333496, 1.5030333995819092, 1.395347237586975, 1.639288306236267, 1.366615891456604, 1.583027720451355, 1.5923789739608765, 1.5880597829818726, 1.8972200155258179, 1.049880027770996, 1.3090558052062988, 1.832811951637268, 1.231062889099121, 1.4205354452133179, 0.6987128257751465, 1.3823658227920532, 1.4012686014175415, 1.7032842636108398, 1.7534408569335938, 1.9114954471588135, 2.1270945072174072, 1.1860978603363037, 1.4713926315307617, 2.4362730979919434, 2.3701205253601074, 2.020280599594116, 2.0527870655059814, 1.409841775894165, 1.9669910669326782, 1.5061314105987549, 1.1584038734436035, 1.387137770652771, 1.3993829488754272, 1.382010817527771, 1.8701515197753906, 1.331897258758545, 1.2899515628814697, 0.8545099496841431, 1.1632201671600342, 0.8934351801872253, 2.0339765548706055, 1.7461919784545898, 1.1339495182037354, 1.2561285495758057, 1.3212352991104126, 1.3911913633346558, 1.8335931301116943, 1.375787615776062, 0.9081152081489563, 1.957161784172058, 1.3760480880737305, 2.003842353820801, 0.9992182850837708, 1.4780575037002563, 1.8122323751449585, 2.8743255138397217, 0.9157434701919556, 0.6658881902694702, 1.4904594421386719, 1.6355575323104858, 0.7903797626495361, 2.0931057929992676, 1.18948495388031, 1.5416854619979858, 0.7258516550064087, 1.1267173290252686, 1.6245867013931274, 0.817912757396698, 0.9567394256591797, 1.4667551517486572, 0.8934863209724426, 1.2015330791473389, 1.775433897972107, 1.509769082069397, 1.1646559238433838, 1.8064403533935547, 0.8028196692466736, 1.6957143545150757, 1.234364628791809, 1.6451903581619263, 1.0692925453186035, 1.693029761314392, 1.2665293216705322, 1.5869287252426147, 1.1622750759124756, 0.7030706405639648, 1.0610665082931519, 1.1563080549240112, 1.7925676107406616, 2.2933547496795654, 1.9604097604751587, 1.3128451108932495, 1.2639110088348389, 1.8521898984909058, 1.6203463077545166, 1.1614739894866943, 1.2762447595596313, 1.3720512390136719, 1.7716012001037598, 0.9163815379142761, 2.0454673767089844, 1.0067219734191895, 1.3458797931671143, 1.255213737487793, 1.687961220741272, 1.4516481161117554, 1.3851161003112793, 1.7396373748779297, 1.6707566976547241, 1.173607587814331, 0.8834599256515503, 2.48960280418396, 215.062255859375, 55.71072006225586, 175.52061462402344, 33.4818115234375, 73.942138671875, 109.08734130859375, 182.46820068359375, 55.999847412109375, 102.8973617553711, 46.710487365722656, 180.73605346679688, 37.75491714477539, 65.44731140136719, 59.68423843383789, 48.755462646484375, 45.99213790893555, 36.79922103881836, 61.277679443359375, 152.8204803466797, 27.084753036499023, 61.410400390625, 76.316650390625, 78.3924560546875, 224.38839721679688, 91.29853057861328, 211.03836059570312, 167.12936401367188, 198.6197052001953, 207.24749755859375, 82.85330200195312, 88.550537109375, 78.82081604003906, 39.9925537109375, 102.564453125, 173.95860290527344, 86.1978530883789, 68.67526245117188, 51.76544189453125, 173.6199951171875, 46.59881591796875, 135.45025634765625, 85.14710998535156, 127.66193389892578, 24.026445388793945, 107.3070068359375, 30.438383102416992, 49.98651885986328, 27.96750831604004, 92.04976654052734, 135.18408203125, 33.54876708984375, 165.318603515625, 36.00869369506836, 29.780738830566406, 44.478084564208984, 44.82073974609375, 98.83023071289062, 182.5148468017578, 35.65557861328125, 174.15383911132812, 106.28211975097656, 153.33627319335938, 120.65731811523438, 241.3435821533203, 30.357938766479492, 30.036762237548828, 160.17941284179688, 37.827030181884766, 41.18328857421875, 167.6955108642578, 82.8411865234375, 73.5406494140625, 182.26055908203125, 105.1888427734375, 129.18173217773438, 196.75450134277344, 42.83218002319336, 64.890380859375, 270.7841491699219, 179.54299926757812, 140.28271484375, 23.749359130859375, 89.90601348876953, 85.99932098388672, 45.9677734375, 123.774658203125, 45.546546936035156, 203.53565979003906, 157.12738037109375, 134.07293701171875, 89.58110809326172, 26.849184036254883, 40.3135986328125, 75.4312744140625, 154.91470336914062, 136.7845458984375, 99.53018951416016, 72.0771255493164, 65.12948608398438, 23.6915283203125, 32.189945220947266, 29.91802978515625, 219.37635803222656, 61.91887664794922, 85.69918060302734, 124.08099365234375, 34.65155029296875, 91.0799560546875, 25.7584228515625, 123.46144104003906, 187.84388732910156, 24.434555053710938, 92.72977447509766, 131.1103515625, 36.24470901489258, 49.446624755859375, 43.38633728027344, 196.3514862060547, 243.6102294921875, 47.578739166259766, 183.7951202392578, 79.2964859008789, 173.5568389892578, 51.62980270385742, 98.14631652832031, 83.26838684082031, 25.81775665283203, 37.65018081665039, 18.880859375, 137.0087127685547, 39.22011184692383, 161.43441772460938, 107.71966552734375, 124.4389419555664, 63.84900665283203, 74.00469207763672, 122.08037567138672, 135.55918884277344, 175.07177734375, 93.59886169433594, 97.44808197021484, 65.36981201171875, 99.2537612915039, 110.12870025634766, 139.69981384277344, 68.95355224609375, 31.382369995117188, 115.33806610107422, 234.6099395751953, 212.43577575683594, 181.4703826904297, 26.56280517578125, 96.72918701171875, 234.44268798828125, 164.0272979736328, 195.9898223876953, 236.92919921875, 140.56790161132812, 27.6160888671875, 128.30239868164062, 53.40723419189453, 62.6435661315918, 140.54217529296875, 264.59979248046875, 32.23779296875, 103.0057373046875, 198.1625518798828, 115.04964447021484, 59.65518569946289, 51.31819152832031, 142.28402709960938, 150.7816619873047, 129.3841552734375, 163.93515014648438, 182.2885284423828, 37.879119873046875, 59.162811279296875, 56.344539642333984, 159.1507568359375, 143.61741638183594, 127.38275146484375, 257.93316650390625, 73.84539794921875, 62.55612564086914, 85.1322021484375, 199.05870056152344, 105.73138427734375, 26.04388427734375, 26.08599853515625, 58.22644805908203, 33.525390625, 63.45087432861328, 68.15653228759766, 200.8377685546875, 119.80997467041016, 58.65188217163086, 26.43309783935547, 129.5915985107422, 100.8802490234375, 52.796199798583984, 83.6105728149414, 21.8170166015625, 83.57681274414062, 57.87409210205078, 56.935829162597656, 106.43462371826172, 57.288299560546875, 204.9580078125, 106.24896240234375, 160.50987243652344, 92.05107879638672, 244.83352661132812, 199.7640380859375, 111.49327850341797, 61.215633392333984, 59.2725830078125, 163.33799743652344, 41.93862533569336, 43.858699798583984, 86.35918426513672, 91.08164978027344, 58.50796127319336, 99.25240325927734, 104.45001983642578, 121.12890625, 21.237518310546875, 142.68353271484375, 37.92486572265625, 82.81246948242188, 137.46104431152344, 43.854217529296875, 233.2397918701172, 187.4239044189453, 53.71731185913086, 65.88066864013672, 30.25611686706543, 227.922607421875, 173.6590576171875, 126.20916748046875, 155.6273193359375, 37.09804916381836, 82.30484008789062, 166.9833984375, 32.14349365234375, 44.3052978515625, 87.38822174072266, 201.0751495361328, 111.80840301513672, 101.1346435546875, 39.537879943847656, 257.27716064453125, 113.18017578125, 42.4970588684082, 118.53970336914062, 147.76593017578125, 87.5798110961914, 223.68307495117188, 244.0595245361328, 337.7195739746094, 58.37473678588867, 205.1351776123047, 186.72418212890625, 86.04813385009766, 22.29571533203125, 234.0596466064453, 33.2957763671875, 229.1595458984375, 195.6953125, 207.2900390625, 106.39513397216797, 25.523193359375, 150.37757873535156, 115.34783935546875, 119.3402328491211, 191.35159301757812, 79.60781860351562, 173.51486206054688, 105.08978271484375, 187.2373046875, 22.90557861328125, 64.90709686279297, 83.0959243774414, 216.563232421875, 157.0333709716797, 75.86322021484375, 149.080810546875, 175.38818359375, 75.06629943847656, 99.06746673583984, 42.128055572509766, 83.92427825927734, 79.49330139160156, 115.2288818359375, 59.28240966796875, 63.45108413696289, 57.63735580444336, 218.76971435546875, 226.161865234375, 42.07712173461914, 137.0890655517578, 3.122666597366333, 3.0303261280059814, 3.7041196823120117, 2.1179535388946533, 3.178088426589966, 2.8042404651641846, 3.274420738220215, 2.802933931350708, 3.4138381481170654, 2.3516886234283447, 2.82895565032959, 2.174689531326294, 3.6458740234375, 2.8368539810180664, 2.452136993408203, 3.2509965896606445, 2.685300588607788, 1.2713900804519653, 1.6098908185958862, 3.2284252643585205, 3.2205793857574463, 3.8628437519073486, 3.2566521167755127, 1.792454481124878, 2.2078497409820557, 1.208089828491211, 2.57340145111084, 2.084686517715454, 2.3301239013671875, 2.9436159133911133, 2.31734037399292, 2.1040945053100586, 2.7043890953063965, 2.955226182937622, 2.892043352127075, 2.9218547344207764, 1.2239437103271484, 2.814114809036255, 2.2598466873168945, 2.9847936630249023, 2.4240100383758545, 2.3522050380706787, 2.1473143100738525, 2.2036828994750977, 2.777850389480591, 2.3487000465393066, 3.9567577838897705, 3.49375057220459, 2.5732812881469727, 2.3098649978637695, 1.9602220058441162, 2.31732439994812, 3.415295362472534, 2.394845724105835, 1.5292710065841675, 3.081866502761841, 1.9339040517807007, 2.320815086364746, 2.5332536697387695, 2.758862257003784, 2.182520866394043, 1.7663519382476807, 2.59757399559021, 2.486788749694824, 2.851644515991211, 2.9139299392700195, 1.6903877258300781, 1.048966407775879, 1.8124370574951172, 2.802882432937622, 1.7635226249694824, 2.2300941944122314, 1.8148199319839478, 1.6953182220458984, 1.635970115661621, 2.3046255111694336, 2.28780460357666, 3.5046050548553467, 2.214392900466919, 3.06478214263916, 2.869558572769165, 2.507380485534668, 1.4543437957763672, 2.8468029499053955, 2.5976247787475586, 2.052487373352051, 1.542907953262329, 2.2693891525268555, 1.5870667695999146, 1.8674896955490112, 1.4273176193237305, 1.4164953231811523, 1.803552508354187, 2.0418701171875, 3.373417854309082, 2.2633309364318848, 2.14212703704834, 3.4242162704467773, 3.1585967540740967, 1.9477938413619995, 3.6736345291137695, 2.1763195991516113, 2.97629451751709, 1.3951081037521362, 1.8927854299545288, 2.8603005409240723, 2.0590105056762695, 2.0339608192443848, 2.7040340900421143, 2.6104376316070557, 3.0923967361450195, 3.45754075050354, 2.448742389678955, 2.8547539710998535, 3.625748872756958, 1.4691215753555298, 3.9132580757141113, 1.684096336364746, 2.772496223449707, 1.4359440803527832, 2.694293737411499, 3.7182955741882324, 3.2827274799346924, 1.1108355522155762, 2.5427441596984863, 2.463578224182129, 2.6866369247436523, 3.370262622833252, 2.782219886779785, 2.739208936691284, 3.156083345413208, 3.149916410446167, 2.526125907897949, 1.6890623569488525, 1.9509203433990479, 2.3793351650238037, 2.190512180328369, 2.365973472595215, 3.847476005554199, 2.8409581184387207, 1.5434194803237915, 2.247478485107422, 3.615891695022583, 2.833362102508545, 2.618715763092041, 2.9884440898895264, 2.9018285274505615, 1.8956502676010132, 2.41829776763916, 2.143678665161133, 2.209080696105957, 2.606618881225586, 1.7604730129241943, 2.818956136703491, 3.68145489692688, 2.272263526916504, 1.7687691450119019, 3.1605236530303955, 3.8077898025512695, 2.582049608230591, 2.0137815475463867, 3.491835832595825, 2.3519930839538574, 3.4508562088012695, 1.6132535934448242, 2.68662428855896, 2.162850856781006, 2.1259870529174805, 2.6409764289855957, 2.7106502056121826, 3.0212793350219727, 2.9197838306427, 2.2014753818511963, 2.8057663440704346, 2.894253969192505, 3.46440052986145, 2.136232852935791, 1.8727712631225586, 4.163201332092285, 2.6216063499450684, 1.7632821798324585, 2.049605369567871, 2.26834774017334, 1.8575780391693115, 2.041553020477295, 2.899266481399536, 1.4545353651046753, 3.074202299118042, 2.115999221801758, 2.287715196609497, 2.6643388271331787, 2.205845594406128, 2.6730237007141113, 2.537841558456421, 2.8213913440704346, 1.4539921283721924, 1.8713979721069336, 3.467881679534912, 1.486629605293274, 3.778574228286743, 3.2206056118011475, 2.1476869583129883, 2.534791946411133, 2.9471545219421387, 2.6785800457000732, 1.552046775817871, 3.3838329315185547, 3.1825037002563477, 1.3622442483901978, 1.963338851928711, 2.7771317958831787, 2.7551164627075195, 2.129474639892578, 1.7400866746902466, 2.892751932144165, 2.9024078845977783, 1.9914294481277466, 1.847554326057434, 2.378465175628662, 2.0733144283294678, 2.394373893737793, 1.2275696992874146, 2.697406053543091, 1.8887947797775269, 2.70231032371521, 2.6137359142303467, 3.486541748046875, 1.7951383590698242, 3.4056994915008545, 2.208024024963379, 3.5816051959991455, 2.3573830127716064, 2.831000328063965, 1.8603878021240234, 1.5897245407104492, 2.277359962463379, 2.5355966091156006, 2.577476978302002, 1.3873831033706665, 3.2039198875427246, 2.9113922119140625, 2.159513235092163, 1.7057380676269531, 2.217205762863159, 2.5434482097625732, 2.346587657928467, 2.1515321731567383, 2.211961269378662, 2.430514097213745, 1.952853798866272, 1.7213797569274902, 2.5264501571655273, 3.7176408767700195, 1.8206180334091187, 3.3996856212615967, 2.4613003730773926, 1.6630167961120605, 3.711916923522949, 3.0965259075164795, 2.5957250595092773, 2.2652578353881836, 3.3623034954071045, 1.969172477722168, 2.320688247680664, 3.5502521991729736, 3.006913423538208, 3.603853702545166, 1.6020442247390747, 2.4915072917938232, 1.9019440412521362, 1.5278180837631226, 3.458909749984741, 3.0435917377471924, 2.734086751937866, 2.706716537475586, 2.428839683532715, 2.3367412090301514, 2.0954573154449463, 1.874953269958496, 2.173753499984741, 2.2258551120758057, 2.37786602973938, 3.0775272846221924, 1.9897500276565552, 2.5457377433776855, 3.151651620864868, 2.100231170654297, 2.871558427810669, 2.1538078784942627, 2.7902615070343018, 3.4064838886260986, 2.8863213062286377, 3.0235893726348877, 1.7433749437332153, 2.920076847076416, 2.1890900135040283, 1.7631462812423706, 1.9537365436553955, 3.7279441356658936, 2.848067045211792, 0.17539596557617188, 0.15789751708507538, 0.22596648335456848, 0.23521295189857483, 0.16179867088794708, 0.14734801650047302, 0.20146386325359344, 0.197459414601326, 0.13900429010391235, 0.15981483459472656, 0.2010057419538498, 0.14424528181552887, 0.17833293974399567, 0.19907912611961365, 0.13995900750160217, 0.1718178540468216, 0.16191723942756653, 0.16353583335876465, 0.22240598499774933, 0.18349862098693848, 0.1638961136341095, 0.15251721441745758, 0.19715796411037445, 0.18096625804901123, 0.11261491477489471, 0.11810310184955597, 0.15371711552143097, 0.1964980661869049, 0.14700397849082947, 0.1307717263698578, 0.131967693567276, 0.19642329216003418, 0.17540860176086426, 0.20889508724212646, 0.2178219109773636, 0.25677022337913513, 0.12343259900808334, 0.1537519097328186, 0.2768191993236542, 0.15326711535453796, 0.10261797904968262, 0.18145738542079926, 0.1648569256067276, 0.20217366516590118, 0.1651158630847931, 0.16384540498256683, 0.15986114740371704, 0.1562853306531906, 0.20296062529087067, 0.22076071798801422, 0.1875983029603958, 0.19387942552566528, 0.16947299242019653, 0.20217609405517578, 0.19758830964565277, 0.19277805089950562, 0.17825926840305328, 0.169677734375, 0.19861911237239838, 0.11875585466623306, 0.13928374648094177, 0.19932842254638672, 0.19367249310016632, 0.15113061666488647, 0.1373153179883957, 0.19927115738391876, 0.17690634727478027, 0.15127751231193542, 0.15558890998363495, 0.16434775292873383, 0.20266856253147125, 0.2627994418144226, 0.16078750789165497, 0.093167744576931, 0.2700943350791931, 0.16995185613632202, 0.12978287041187286, 0.11687196791172028, 0.23891475796699524, 0.2856556177139282, 0.17225287854671478, 0.2271662801504135, 0.2174537181854248, 0.08845555782318115, 0.1371479630470276, 0.1817554384469986, 0.2495935708284378, 0.19846610724925995, 0.2400134801864624, 0.1833207607269287, 0.17004349827766418, 0.20340962707996368, 0.2067558616399765, 0.2333415299654007, 0.2137834131717682, 0.2161782830953598, 0.22038134932518005, 0.1542884260416031, 0.11640787124633789, 0.24894388020038605, 0.2460356503725052, 0.15741229057312012, 0.1417686939239502, 0.15700210630893707, 0.19829845428466797, 0.18744392693042755, 0.1858820915222168, 0.17988145351409912, 0.1698346883058548, 0.22009719908237457, 0.24122214317321777, 0.1523560881614685, 0.15442444384098053, 0.08280414342880249, 0.18705160915851593, 0.2206300050020218, 0.1867416650056839, 0.18760497868061066, 0.19350279867649078, 0.2370891571044922, 0.2432907074689865, 0.12671010196208954, 0.17472968995571136, 0.15176555514335632, 0.19752754271030426, 0.1167970821261406, 0.1521003246307373, 0.14905257523059845, 0.16162443161010742, 0.12431201338768005, 0.19615210592746735, 0.16795165836811066, 0.25147613883018494, 0.09786537289619446, 0.20410171151161194, 0.2247331440448761, 0.20063349604606628, 0.1294737011194229, 0.1614353507757187, 0.1782459020614624, 0.14797303080558777, 0.17155463993549347, 0.2891443073749542, 0.15358838438987732, 0.1997959464788437, 0.2654237449169159, 0.14089566469192505, 0.11309456825256348, 0.15950600802898407, 0.13894565403461456, 0.16641181707382202, 0.23755580186843872, 0.21289308369159698, 0.20604026317596436, 0.22366046905517578, 0.17356662452220917, 0.1825781911611557, 0.24725845456123352, 0.16407878696918488, 0.14039850234985352, 0.21778033673763275, 0.152633935213089, 0.13503040373325348, 0.1972600519657135, 0.18324990570545197, 0.1147245541214943, 0.10489141196012497, 0.23421505093574524, 0.18495608866214752, 0.22214074432849884, 0.1822543442249298, 0.20412786304950714, 0.21295319497585297, 0.12843450903892517, 0.12208020687103271, 0.16777347028255463, 0.0990203246474266, 0.193506121635437, 0.170484259724617, 0.182565838098526, 0.10437843203544617, 0.14810186624526978, 0.18688461184501648, 0.1836351752281189, 0.144364133477211, 0.15841087698936462, 0.19216592609882355, 0.19072669744491577, 0.23209932446479797, 0.16200362145900726, 0.18460984528064728, 0.22226783633232117, 0.22777718305587769, 0.18419891595840454, 0.14416570961475372, 0.17006675899028778, 0.18298648297786713, 0.22751478850841522, 0.19731898605823517, 0.16015075147151947, 0.17952056229114532, 0.22211787104606628, 0.1325959712266922, 0.10299581289291382, 0.2764110267162323, 0.23792342841625214, 0.16799375414848328, 0.15548932552337646, 0.20249851047992706, 0.209599107503891, 0.1776232123374939, 0.24686145782470703, 0.11180772632360458, 0.11017149686813354, 0.23208019137382507, 0.1451360434293747, 0.2098345011472702, 0.16854381561279297, 0.14850382506847382, 0.10031524300575256, 0.16128922998905182, 0.16461025178432465, 0.16552592813968658, 0.17973309755325317, 0.15640109777450562, 0.19933034479618073, 0.1408526599407196, 0.18299634754657745, 0.12336844205856323, 0.1131618320941925, 0.1747516393661499, 0.2104758471250534, 0.20553378760814667, 0.2590934634208679, 0.1712450385093689, 0.135428324341774, 0.24700501561164856, 0.165973961353302, 0.16152635216712952, 0.2345670610666275, 0.2235478311777115, 0.1280045062303543, 0.22401674091815948, 0.0924975648522377, 0.1724141240119934, 0.11478442698717117, 0.20956291258335114, 0.175363689661026, 0.154973104596138, 0.19945621490478516, 0.22338666021823883, 0.12488839775323868, 0.1746446192264557, 0.19712458550930023, 0.23615339398384094, 0.21758556365966797, 0.2149183601140976, 0.1789560616016388, 0.224837064743042, 0.2137766182422638, 0.12852336466312408, 0.2277992218732834, 0.28751707077026367, 0.20734558999538422, 0.154688760638237, 0.1956496387720108, 0.15703387558460236, 0.10832347720861435, 0.14439037442207336, 0.1403486728668213, 0.17710570991039276, 0.1591091752052307, 0.21913352608680725, 0.16784824430942535, 0.160368874669075, 0.17250803112983704, 0.17080387473106384, 0.18507152795791626, 0.209665447473526, 0.21074575185775757, 0.18490350246429443, 0.14541220664978027, 0.2430008202791214, 0.2060176432132721, 0.17654752731323242, 0.17476756870746613, 0.15916851162910461, 0.2047683298587799, 0.20971553027629852, 0.17667971551418304, 0.19283349812030792, 0.18323267996311188, 0.1642448753118515, 0.13894572854042053, 0.152052640914917, 0.25039249658584595, 0.13730058073997498, 0.1602901667356491, 0.17633602023124695, 0.11741023510694504, 2.341111898422241, 1.6589314937591553, 1.5011001825332642, 1.7339718341827393, 1.8333593606948853, 0.9478034973144531, 1.8334041833877563, 1.4000506401062012, 1.6106839179992676, 1.8801004886627197, 1.9784481525421143, 1.1133095026016235, 1.3103379011154175, 1.1617082357406616, 1.3261381387710571, 1.5944565534591675, 1.8516677618026733, 1.2852853536605835, 1.4021317958831787, 1.3802013397216797, 1.4257471561431885, 1.8674501180648804, 1.6208604574203491, 1.0340913534164429, 1.5553998947143555, 1.7177276611328125, 1.7092220783233643, 1.3566460609436035, 1.8268013000488281, 1.4205070734024048, 1.3649685382843018, 2.202958583831787, 1.5534547567367554, 1.1872429847717285, 1.6355828046798706, 1.0520917177200317, 1.584917664527893, 1.2768323421478271, 1.1066161394119263, 1.4164024591445923, 1.5807104110717773, 2.281252145767212, 1.1338527202606201, 1.420383095741272, 0.5744530558586121, 1.0812870264053345, 1.2160271406173706, 1.4083459377288818, 2.086268424987793, 1.0128105878829956, 1.1926335096359253, 1.21983003616333, 0.9357421398162842, 1.5848743915557861, 1.932002067565918, 1.3123054504394531, 2.3315553665161133, 0.9566224217414856, 1.823722243309021, 1.4525240659713745, 1.3265997171401978, 0.7329352498054504, 1.782063364982605, 1.8566118478775024, 2.3593831062316895, 1.152605414390564, 1.53264582157135, 1.509812593460083, 1.323799967765808, 1.8584617376327515, 1.4229995012283325, 1.93376886844635, 1.7061538696289062, 0.7761239409446716, 1.3342748880386353, 1.448250651359558, 0.8530582785606384, 1.6135878562927246, 1.8688629865646362, 1.5898808240890503, 1.7153258323669434, 1.8062516450881958, 1.1890206336975098, 1.9515011310577393, 1.4335962533950806, 1.2809176445007324, 1.298950433731079, 0.924923837184906, 2.135864019393921, 1.103922963142395, 0.8014861941337585, 1.613890290260315, 1.8816502094268799, 1.4193605184555054, 0.8408644199371338, 1.0838127136230469, 1.0685573816299438, 1.0338287353515625, 1.541894555091858, 1.9092867374420166, 1.7178159952163696, 1.1278373003005981, 1.7390047311782837, 1.3778181076049805, 1.6500883102416992, 1.446521282196045, 1.2486419677734375, 1.4979517459869385, 0.839941143989563, 1.044885277748108, 1.3764753341674805, 2.4298477172851562, 1.8609930276870728, 1.872697353363037, 1.7585961818695068, 2.2073190212249756, 1.3670991659164429, 1.994055151939392, 0.968362033367157, 1.277138590812683, 1.7695809602737427, 0.9485686421394348, 1.1307997703552246, 2.3342044353485107, 0.8988059163093567, 1.8125413656234741, 2.0411953926086426, 1.2917321920394897, 1.0256134271621704, 1.5574203729629517, 0.9309741258621216, 1.8806275129318237, 1.5266952514648438, 1.9529470205307007, 1.2406237125396729, 1.256103277206421, 1.9084383249282837, 1.7814178466796875, 1.2418599128723145, 2.2872602939605713, 1.5192123651504517, 1.2182650566101074, 2.0725038051605225, 1.6416900157928467, 1.7321701049804688, 1.1854978799819946, 1.3903396129608154, 1.8678315877914429, 0.8113629221916199, 1.4438003301620483, 1.8680082559585571, 1.1656107902526855, 1.2231967449188232, 1.3444207906723022, 1.7931509017944336, 1.0477877855300903, 1.7277958393096924, 2.3966386318206787, 1.4988796710968018, 1.5256004333496094, 1.302379846572876, 1.5718116760253906, 1.4495830535888672, 1.7668325901031494, 0.9881709218025208, 1.6945240497589111, 0.9704645276069641, 1.0289992094039917, 1.4901604652404785, 1.3056893348693848, 1.1778864860534668, 1.6180633306503296, 1.8565946817398071, 1.452789306640625, 1.5301681756973267, 1.2098290920257568, 1.3071457147598267, 1.1117216348648071, 1.6529693603515625, 1.053053855895996, 1.1686245203018188, 2.0318148136138916, 1.601666808128357, 1.32793390750885, 2.0146493911743164, 1.8784326314926147, 1.9496721029281616, 1.3161413669586182, 0.99029141664505, 1.9296826124191284, 1.0005519390106201, 1.7745498418807983, 2.3676185607910156, 2.539567708969116, 1.1508516073226929, 1.637683391571045, 2.6260697841644287, 1.3426910638809204, 1.2704603672027588, 1.435323715209961, 1.994728684425354, 1.45555579662323, 0.9529466032981873, 1.3888812065124512, 1.9043585062026978, 1.968111276626587, 1.5153582096099854, 2.3081719875335693, 1.6775922775268555, 1.6111719608306885, 0.8516312837600708, 0.8019143342971802, 2.1296234130859375, 1.8721262216567993, 2.2690324783325195, 1.2443273067474365, 1.4510644674301147, 2.872589588165283, 1.0015569925308228, 1.831331491470337, 1.0978186130523682, 1.8236204385757446, 1.1808702945709229, 1.2019680738449097, 2.072525978088379, 1.545235276222229, 1.4018383026123047, 1.2371163368225098, 1.1057466268539429, 1.853538155555725, 1.260162591934204, 1.511735200881958, 1.2034764289855957, 1.9368247985839844, 0.6205967664718628, 2.2769460678100586, 1.1024008989334106, 3.027142286300659, 1.6264704465866089, 0.979661226272583, 1.8933563232421875, 1.0928714275360107, 1.2425036430358887, 1.6851471662521362, 1.5288206338882446, 1.9298670291900635, 1.128757357597351, 1.0670794248580933, 1.6865969896316528, 1.4380806684494019, 1.3775851726531982, 1.8416193723678589, 1.5511919260025024, 1.3635119199752808, 2.312595844268799, 1.6465966701507568, 1.6196844577789307, 2.167006492614746, 1.645225167274475, 1.902077317237854, 1.15897798538208, 1.4749482870101929, 2.2479147911071777, 1.0361356735229492, 1.7151222229003906, 0.9324362874031067, 0.642691969871521, 0.9090192914009094, 1.1078182458877563, 1.224193811416626, 1.8181887865066528, 1.4161592721939087, 1.5465433597564697, 1.6883553266525269, 2.518625020980835, 0.9165424704551697, 1.079674243927002, 2.539320707321167, 1.6295305490493774, 2.249021053314209, 1.8292614221572876, 1.271323561668396, 1.3335670232772827, 1.4853883981704712, 1.6464658975601196, 1.681976556777954, 1.9371944665908813, 2.0219359397888184, 1.7954885959625244, 1.8220449686050415, 1.6248124837875366, 0.8804481029510498, 1.5584206581115723, 2.0284881591796875, 1.3019912242889404, 1.3433054685592651, 1.7756034135818481, 1.11494779586792, 0.9320853352546692, 1.0148296356201172, 64.12261199951172, 79.28286743164062, 173.0535888671875, 62.4434814453125, 70.1661376953125, 67.98072052001953, 87.58916473388672, 107.5023422241211, 186.27880859375, 98.3910140991211, 70.18020629882812, 130.8334503173828, 84.43830108642578, 32.81573486328125, 97.400390625, 154.83511352539062, 43.334598541259766, 144.03575134277344, 68.11370849609375, 94.82771301269531, 111.20757293701172, 224.86045837402344, 158.03721618652344, 342.4269104003906, 100.78128814697266, 70.20404815673828, 105.46307373046875, 157.00621032714844, 237.30218505859375, 112.07929229736328, 56.05671310424805, 137.17347717285156, 176.61196899414062, 24.503421783447266, 135.35020446777344, 72.21179962158203, 98.60900115966797, 96.434814453125, 127.64749908447266, 130.00765991210938, 199.0902557373047, 49.07318115234375, 95.62095642089844, 165.0719451904297, 32.771305084228516, 24.65325927734375, 52.13794708251953, 233.06700134277344, 222.46875, 129.514404296875, 68.17414855957031, 31.98297119140625, 76.13479614257812, 116.90790557861328, 55.085174560546875, 125.1107177734375, 94.85317993164062, 37.604705810546875, 152.18374633789062, 204.1746368408203, 181.0153350830078, 131.19076538085938, 20.21087646484375, 146.64666748046875, 21.908353805541992, 74.30400848388672, 100.67042541503906, 173.2728271484375, 106.85025024414062, 77.13790893554688, 23.625125885009766, 89.52261352539062, 162.44976806640625, 35.182926177978516, 256.6416015625, 86.98291015625, 135.67288208007812, 191.91758728027344, 236.21697998046875, 45.39126968383789, 142.2213592529297, 58.8487548828125, 144.39828491210938, 95.68511199951172, 103.14474487304688, 188.0322265625, 35.58319854736328, 49.79730224609375, 188.24737548828125, 134.04852294921875, 113.50464630126953, 130.32127380371094, 94.90692138671875, 130.6351318359375, 140.97445678710938, 173.18276977539062, 193.45274353027344, 38.89593505859375, 158.0592803955078, 191.5272674560547, 37.13739013671875, 53.56365966796875, 49.991180419921875, 150.60360717773438, 124.2929458618164, 145.49546813964844, 234.19122314453125, 40.28164291381836, 203.2029266357422, 196.1102752685547, 339.80694580078125, 35.16351318359375, 62.00663757324219, 39.77911376953125, 60.48529052734375, 54.79655075073242, 77.95101165771484, 126.52001953125, 69.37631225585938, 39.70465087890625, 211.4852294921875, 72.47956085205078, 291.8583984375, 171.4888458251953, 30.92997169494629, 26.617816925048828, 32.42007064819336, 114.71893310546875, 197.0414276123047, 95.86222076416016, 45.15956115722656, 108.53900146484375, 180.08323669433594, 61.27509689331055, 147.84097290039062, 56.5191650390625, 173.1689453125, 38.69131088256836, 100.4462890625, 70.5010986328125, 127.24673461914062, 213.2622833251953, 85.48735809326172, 195.47015380859375, 193.9521026611328, 29.593114852905273, 114.27153778076172, 55.39113998413086, 28.91156005859375, 116.1051254272461, 112.68643951416016, 109.276123046875, 63.46613693237305, 41.47623825073242, 205.51475524902344, 191.1693878173828, 167.0176544189453, 76.78707885742188, 134.92828369140625, 90.57373046875, 77.5321044921875, 161.22840881347656, 75.30160522460938, 83.11994171142578, 28.29599952697754, 95.25899505615234, 107.06475067138672, 104.47440338134766, 81.35061645507812, 37.64574432373047, 191.05967712402344, 279.06640625, 29.34048843383789, 66.18134307861328, 115.09661865234375, 171.0664825439453, 150.756103515625, 53.53168869018555, 96.82633209228516, 146.811279296875, 174.1815185546875, 153.46591186523438, 125.63201904296875, 126.58056640625, 237.1312255859375, 109.529296875, 62.11855697631836, 188.2146453857422, 83.91815185546875, 119.85700988769531, 42.87195587158203, 186.94729614257812, 161.16180419921875, 146.82284545898438, 61.379432678222656, 234.7967987060547, 108.5408935546875, 60.40486526489258, 114.08695220947266, 137.88214111328125, 72.96444702148438, 132.73110961914062, 58.27168655395508, 44.60150146484375, 33.969818115234375, 113.58642578125, 35.79763412475586, 33.36172103881836, 35.29937744140625, 118.50646209716797, 111.9549560546875, 24.066503524780273, 30.6671142578125, 158.73593139648438, 20.735614776611328, 81.37960052490234, 155.24302673339844, 24.99603271484375, 145.62428283691406, 218.17893981933594, 67.43063354492188, 85.36406707763672, 31.66161346435547, 126.93228149414062, 175.77268981933594, 146.98448181152344, 39.53887939453125, 30.652650833129883, 190.2908935546875, 132.93869018554688, 217.06040954589844, 58.29833984375, 127.44316864013672, 223.09423828125, 150.3587646484375, 103.43081665039062, 121.53851318359375, 65.24188232421875, 65.31784057617188, 43.95991134643555, 155.07191467285156, 105.5667724609375, 59.3521728515625, 33.93024444580078, 63.779998779296875, 102.26661682128906, 90.8805923461914, 59.64665985107422, 145.94378662109375, 65.53909301757812, 38.491233825683594, 39.907630920410156, 143.6361846923828, 210.2504119873047, 116.14585876464844, 102.46587371826172, 86.37088775634766, 82.81195831298828, 42.100345611572266, 75.953125, 118.78704833984375, 28.761735916137695, 60.49689483642578, 110.03079986572266, 189.3831024169922, 72.38461303710938, 214.1128692626953, 80.13323974609375, 53.44218063354492, 176.36331176757812, 82.7181167602539, 47.029109954833984, 145.76470947265625, 67.04995727539062, 147.39126586914062, 75.3655776977539, 178.0049591064453, 18.419464111328125, 45.937713623046875, 40.76507568359375, 273.56298828125, 263.6383056640625, 74.34664916992188, 243.655029296875, 93.07464599609375, 65.15455627441406, 96.92724609375, 133.37738037109375, 117.45023345947266, 227.9685516357422, 212.3145294189453, 88.90238189697266, 143.77691650390625, 172.28640747070312, 109.3993148803711, 66.6751480102539, 146.60289001464844, 56.458343505859375, 78.369384765625, 152.94949340820312, 2.784430980682373, 2.663273811340332, 3.304227113723755, 2.4933366775512695, 2.2003135681152344, 3.513423442840576, 1.716933250427246, 2.8060638904571533, 3.7544164657592773, 2.3022639751434326, 3.9202020168304443, 3.5343551635742188, 2.6367712020874023, 2.3144888877868652, 3.4880099296569824, 1.6518974304199219, 2.411893844604492, 2.8521578311920166, 2.2844936847686768, 1.7944469451904297, 2.6282665729522705, 2.5809643268585205, 2.869133949279785, 2.6729142665863037, 3.940648078918457, 1.355208396911621, 2.283001184463501, 2.9741387367248535, 2.0504982471466064, 2.182623863220215, 1.881832242012024, 2.570770740509033, 2.231869697570801, 2.7641093730926514, 3.274750232696533, 1.66588294506073, 2.3578147888183594, 2.819972515106201, 2.563506603240967, 2.7779181003570557, 2.5773468017578125, 2.02706241607666, 2.306065559387207, 1.869227409362793, 3.560276985168457, 2.093000650405884, 2.027440071105957, 3.035670042037964, 2.4815073013305664, 1.2917412519454956, 2.576568603515625, 2.2543935775756836, 1.4383244514465332, 3.521331310272217, 2.2530858516693115, 2.663682222366333, 1.569091796875, 2.6297078132629395, 2.2396841049194336, 2.0831868648529053, 2.4820337295532227, 2.829291582107544, 2.6708767414093018, 2.189969539642334, 3.9133481979370117, 1.8567020893096924, 1.4752202033996582, 1.0645055770874023, 3.1357452869415283, 2.6515111923217773, 2.2467703819274902, 4.383571147918701, 2.9435548782348633, 2.3087117671966553, 3.128310441970825, 1.4933332204818726, 3.2374227046966553, 2.0917978286743164, 1.7405251264572144, 2.5830483436584473, 1.7141599655151367, 1.922839641571045, 1.6797819137573242, 2.4163339138031006, 2.7519137859344482, 2.294246196746826, 1.9580281972885132, 1.424407958984375, 2.8487823009490967, 2.3475732803344727, 3.343079090118408, 3.01132869720459, 2.8803083896636963, 1.5962857007980347, 2.465754508972168, 1.2597934007644653, 2.751030206680298, 2.158885955810547, 3.098275661468506, 2.1729304790496826, 2.523493766784668, 2.061450719833374, 2.6760244369506836, 2.736344575881958, 1.2799949645996094, 1.8446584939956665, 3.135361909866333, 2.9268715381622314, 3.1339008808135986, 2.915994167327881, 3.121562957763672, 4.00650691986084, 3.151381254196167, 2.650728702545166, 2.9650533199310303, 2.389009714126587, 1.998346209526062, 2.18270206451416, 2.61037540435791, 2.2134926319122314, 2.096222162246704, 2.219040870666504, 2.7753021717071533, 2.255539894104004, 2.178773880004883, 1.6686217784881592, 1.9788178205490112, 2.71639347076416, 2.3601417541503906, 2.430950880050659, 2.281975507736206, 2.4693422317504883, 3.4534006118774414, 2.770939826965332, 2.2676897048950195, 1.6176948547363281, 1.5070247650146484, 2.203436851501465, 1.459857702255249, 2.3059489727020264, 3.5102248191833496, 3.8996801376342773, 1.5800178050994873, 1.5329253673553467, 1.660603642463684, 2.294259548187256, 2.5030603408813477, 1.6200906038284302, 3.0499491691589355, 2.904008150100708, 1.9537173509597778, 2.691545009613037, 2.6088249683380127, 1.871914267539978, 2.161576271057129, 2.038428544998169, 2.8846232891082764, 3.0126237869262695, 2.7403457164764404, 1.639970064163208, 2.2199392318725586, 1.7635526657104492, 1.5911251306533813, 1.6648435592651367, 1.6727526187896729, 2.51216721534729, 2.1669435501098633, 2.619189500808716, 1.680134654045105, 2.544877529144287, 1.9038724899291992, 3.005542039871216, 2.4587695598602295, 1.6908445358276367, 2.4860751628875732, 1.9100500345230103, 2.467434883117676, 1.8810300827026367, 3.5347607135772705, 3.0056591033935547, 1.636667013168335, 2.0456743240356445, 3.4768993854522705, 2.902331590652466, 2.2113847732543945, 3.1212661266326904, 1.804286003112793, 2.8511931896209717, 2.256916046142578, 2.7458159923553467, 2.593278169631958, 3.0483202934265137, 2.790026903152466, 3.147874116897583, 3.0118255615234375, 3.7298052310943604, 1.7934553623199463, 1.7206709384918213, 1.9823487997055054, 2.5806610584259033, 2.430478096008301, 2.9301838874816895, 2.4731342792510986, 2.290351629257202, 2.7444393634796143, 1.9994248151779175, 3.4863691329956055, 1.9858862161636353, 2.7243423461914062, 2.4965908527374268, 2.202796220779419, 2.4754676818847656, 2.686220407485962, 2.9873993396759033, 3.001500368118286, 1.967940330505371, 2.624518632888794, 2.371994972229004, 1.8016480207443237, 2.2007687091827393, 1.4753179550170898, 3.331332206726074, 1.7273969650268555, 2.0192348957061768, 3.370345115661621, 1.822133183479309, 2.5183823108673096, 2.310940742492676, 1.789711594581604, 2.9870970249176025, 2.782451629638672, 1.6527462005615234, 2.5395336151123047, 1.7754029035568237, 2.0351500511169434, 3.12637996673584, 3.245734214782715, 2.861680269241333, 1.459511399269104, 2.61136531829834, 3.286576509475708, 2.6144092082977295, 1.8465690612792969, 2.4625673294067383, 1.8826513290405273, 2.224270820617676, 1.8508999347686768, 3.2594237327575684, 3.40775990486145, 2.337029457092285, 2.1871423721313477, 3.007216691970825, 2.094536781311035, 2.448878049850464, 1.467373013496399, 3.549006938934326, 1.9918622970581055, 1.5153053998947144, 2.5938737392425537, 1.514184832572937, 2.3577470779418945, 2.9091460704803467, 3.303128242492676, 2.0169503688812256, 1.48005211353302, 3.1723926067352295, 2.270176887512207, 2.490725517272949, 2.1305017471313477, 2.496068000793457, 2.1972742080688477, 2.891232490539551, 3.510784864425659, 2.418832540512085, 3.705827236175537, 2.637824058532715, 2.7404732704162598, 2.7243664264678955, 2.9844963550567627, 2.5305864810943604, 3.3798577785491943, 2.576505184173584, 3.1672074794769287, 1.9038420915603638, 3.0499331951141357, 2.58328914642334, 1.55489981174469, 2.6067302227020264, 1.5872100591659546, 1.8581466674804688, 1.4820603132247925, 1.9424413442611694, 2.5590314865112305, 3.559004545211792, 2.8993725776672363, 3.9304332733154297, 2.856537342071533, 2.1192140579223633, 2.0101137161254883, 3.002610445022583, 0.17889072000980377, 0.14724628627300262, 0.22356043756008148, 0.16484947502613068, 0.1779022216796875, 0.174019917845726, 0.20872576534748077, 0.22048141062259674, 0.18834222853183746, 0.2066081166267395, 0.21183587610721588, 0.23950007557868958, 0.1852165162563324, 0.13836035132408142, 0.09576597809791565, 0.2049863040447235, 0.21706469357013702, 0.17380300164222717, 0.2708204686641693, 0.2881278693675995, 0.11879601329565048, 0.22701208293437958, 0.16353270411491394, 0.16056615114212036, 0.14242877066135406, 0.16402912139892578, 0.2219989150762558, 0.1780126541852951, 0.17201213538646698, 0.139788419008255, 0.21201440691947937, 0.19498971104621887, 0.21494796872138977, 0.09030333161354065, 0.21472793817520142, 0.18719911575317383, 0.12377836555242538, 0.1425991952419281, 0.22227561473846436, 0.18138450384140015, 0.13500580191612244, 0.16908010840415955, 0.17380452156066895, 0.19945433735847473, 0.17921440303325653, 0.17036372423171997, 0.23137423396110535, 0.22196708619594574, 0.09460532665252686, 0.1684143841266632, 0.17389555275440216, 0.176621675491333, 0.1797148883342743, 0.12905815243721008, 0.14386515319347382, 0.17855238914489746, 0.17544879019260406, 0.17618907988071442, 0.19203922152519226, 0.1877921223640442, 0.2105693817138672, 0.1763901263475418, 0.23120856285095215, 0.17123278975486755, 0.16178928315639496, 0.19502539932727814, 0.2519550919532776, 0.14532828330993652, 0.16051647067070007, 0.10317391902208328, 0.16883598268032074, 0.16490821540355682, 0.19136103987693787, 0.17438708245754242, 0.27353304624557495, 0.15419961512088776, 0.17671190202236176, 0.2012251615524292, 0.14349037408828735, 0.15741412341594696, 0.2366085946559906, 0.06697118282318115, 0.20253761112689972, 0.2522832751274109, 0.2195708006620407, 0.1702803373336792, 0.1802978515625, 0.23925593495368958, 0.20249225199222565, 0.2240031361579895, 0.12427205592393875, 0.1359347552061081, 0.20025983452796936, 0.1664440929889679, 0.130046084523201, 0.14843331277370453, 0.17147421836853027, 0.21135060489177704, 0.24096529185771942, 0.18139953911304474, 0.166293203830719, 0.1767086386680603, 0.17508170008659363, 0.11752479523420334, 0.19074371457099915, 0.17485448718070984, 0.20117682218551636, 0.1470607966184616, 0.24910880625247955, 0.11568580567836761, 0.16691721975803375, 0.15976086258888245, 0.1250939965248108, 0.15056054294109344, 0.1658998280763626, 0.1283118724822998, 0.13852864503860474, 0.16394604742527008, 0.17969229817390442, 0.18545487523078918, 0.10861948132514954, 0.1807681769132614, 0.1954689770936966, 0.1616508960723877, 0.200057253241539, 0.2084844559431076, 0.15760210156440735, 0.20311252772808075, 0.2257564663887024, 0.21992675960063934, 0.11852703988552094, 0.16661487519741058, 0.23162522912025452, 0.13291293382644653, 0.16736289858818054, 0.2195369154214859, 0.19351661205291748, 0.20579564571380615, 0.1607505828142166, 0.20267482101917267, 0.18210890889167786, 0.19663485884666443, 0.24682176113128662, 0.22509342432022095, 0.16793577373027802, 0.2120288759469986, 0.17131686210632324, 0.17856667935848236, 0.1668061763048172, 0.09891562908887863, 0.20352013409137726, 0.15979821979999542, 0.13859115540981293, 0.1628745198249817, 0.1841069906949997, 0.1357351690530777, 0.1769191324710846, 0.14059066772460938, 0.1896943747997284, 0.17291079461574554, 0.19665201008319855, 0.17142479121685028, 0.1348717212677002, 0.17764392495155334, 0.15401984751224518, 0.2334609478712082, 0.14804482460021973, 0.12504352629184723, 0.2356046438217163, 0.18582256138324738, 0.21399784088134766, 0.2089751958847046, 0.16211751103401184, 0.24123069643974304, 0.23800280690193176, 0.17427876591682434, 0.11596330255270004, 0.21867835521697998, 0.19832190871238708, 0.14980094134807587, 0.18926258385181427, 0.17385132610797882, 0.14276236295700073, 0.1462191343307495, 0.18636679649353027, 0.17569378018379211, 0.16934050619602203, 0.16192317008972168, 0.18671846389770508, 0.18668891489505768, 0.18001137673854828, 0.16143359243869781, 0.22335799038410187, 0.15682794153690338, 0.13705624639987946, 0.1758275181055069, 0.1278059333562851, 0.11634683609008789, 0.11689057946205139, 0.1450352817773819, 0.14050306379795074, 0.13390929996967316, 0.12708036601543427, 0.17832301557064056, 0.2005881816148758, 0.1477641761302948, 0.1109694242477417, 0.19215047359466553, 0.15573012828826904, 0.16415460407733917, 0.21945075690746307, 0.16981665790081024, 0.18511755764484406, 0.1473817229270935, 0.21917305886745453, 0.13492451608181, 0.19456543028354645, 0.23120637238025665, 0.21070967614650726, 0.16828833520412445, 0.22131900489330292, 0.16513687372207642, 0.13589195907115936, 0.1485147476196289, 0.14378812909126282, 0.17463400959968567, 0.15655668079853058, 0.1587049961090088, 0.1645035445690155, 0.12505927681922913, 0.17732469737529755, 0.1807522177696228, 0.15080872178077698, 0.19762393832206726, 0.19170959293842316, 0.11906295269727707, 0.2529185712337494, 0.1694401502609253, 0.13149379193782806, 0.15733684599399567, 0.17608650028705597, 0.1364961415529251, 0.14149706065654755, 0.18247482180595398, 0.15582162141799927, 0.23744648694992065, 0.23034901916980743, 0.18323394656181335, 0.19643233716487885, 0.18696075677871704, 0.3057340979576111, 0.17174750566482544, 0.2099982351064682, 0.07598914206027985, 0.20507945120334625, 0.1371418982744217, 0.1783149093389511, 0.24652822315692902, 0.19575980305671692, 0.15165887773036957, 0.16011697053909302, 0.18931983411312103, 0.1962597668170929, 0.18367137014865875, 0.11720031499862671, 0.2756673991680145, 0.19551536440849304, 0.20333746075630188, 0.1585531234741211, 0.23042096197605133, 0.11358686536550522, 0.23296841979026794, 0.18500171601772308, 0.20636893808841705, 0.2466268092393875, 0.08979985862970352, 0.1846432238817215, 0.27948978543281555, 0.20753830671310425, 0.19612239301204681, 0.22585947811603546, 0.16687415540218353, 0.17937663197517395, 0.15045493841171265, 0.12656572461128235, 0.22251582145690918, 0.13463686406612396, 0.19174474477767944, 0.13557569682598114, 0.19720755517482758, 0.15345068275928497, 0.1961093693971634, 0.18316753208637238, 0.17953507602214813, 0.12616120278835297, 0.1846521645784378, 0.20130233466625214, 0.2116510272026062, 0.21247301995754242, 0.17910130321979523, 1.3137075901031494, 1.6862640380859375, 1.2267653942108154, 1.2568790912628174, 1.263490080833435, 2.2898647785186768, 1.3409473896026611, 0.9817944765090942, 1.3028881549835205, 1.303582787513733, 1.1849640607833862, 1.4532214403152466, 1.2521531581878662, 1.1541706323623657, 1.5721721649169922, 1.908642053604126, 1.85340416431427, 1.5717331171035767, 1.1134544610977173, 1.6471600532531738, 1.8725277185440063, 1.1126328706741333, 0.8424688577651978, 1.6589813232421875, 1.0271553993225098, 1.7022560834884644, 1.6298251152038574, 1.597306489944458, 0.860948383808136, 1.1184144020080566, 1.6256746053695679, 1.7783602476119995, 1.2726775407791138, 1.4098386764526367, 1.9690284729003906, 1.5430160760879517, 0.9045028686523438, 2.180959939956665, 1.13454270362854, 1.0423506498336792, 1.1523618698120117, 2.0521609783172607, 1.0114558935165405, 2.0889732837677, 2.0227038860321045, 1.3135108947753906, 1.8721102476119995, 1.6586138010025024, 1.149716854095459, 1.3377071619033813, 3.07940936088562, 1.7823576927185059, 1.1984939575195312, 1.9797855615615845, 1.3572063446044922, 2.192631721496582, 0.6340103149414062, 1.3821243047714233, 1.305904507637024, 1.9937044382095337, 1.4872204065322876, 1.8691179752349854, 1.8996546268463135, 0.9816328287124634, 2.1471824645996094, 1.0324612855911255, 1.3596454858779907, 1.3283401727676392, 2.0451390743255615, 1.8919689655303955, 1.4828007221221924, 0.911576509475708, 1.2297213077545166, 1.0832096338272095, 1.364788293838501, 1.8718581199645996, 1.7722301483154297, 1.580111026763916, 1.5428822040557861, 1.219564437866211, 1.7641081809997559, 1.4443153142929077, 1.532573938369751, 1.0182782411575317, 1.422579050064087, 1.4320000410079956, 1.211796522140503, 1.9872665405273438, 1.6770880222320557, 1.5034830570220947, 1.5856029987335205, 1.2933117151260376, 1.8979072570800781, 2.1273882389068604, 1.7786269187927246, 1.949926733970642, 1.2242635488510132, 1.3172348737716675, 1.3789929151535034, 1.1171691417694092, 1.4723474979400635, 1.0581642389297485, 1.3729133605957031, 0.8545997142791748, 1.6837899684906006, 1.7744375467300415, 1.447593092918396, 1.3575559854507446, 1.20161771774292, 1.736911416053772, 1.1368563175201416, 1.1187281608581543, 1.2566713094711304, 1.6322542428970337, 1.1944247484207153, 1.7095391750335693, 1.0927834510803223, 2.010009765625, 2.1684954166412354, 1.911664366722107, 1.0080034732818604, 1.5691425800323486, 1.2926342487335205, 1.4651870727539062, 1.6067019701004028, 1.771529197692871, 1.2866570949554443, 1.3675810098648071, 1.740795373916626, 1.146872878074646, 2.186077356338501, 1.8856544494628906, 1.264394998550415, 2.255448818206787, 1.7183277606964111, 1.5875948667526245, 1.159977674484253, 1.6235542297363281, 0.9474108815193176, 2.33359432220459, 2.4292397499084473, 1.462514877319336, 0.9304001927375793, 1.5618765354156494, 1.518424391746521, 1.8667190074920654, 2.0947179794311523, 1.5743917226791382, 2.5264780521392822, 1.654505729675293, 1.5245177745819092, 1.5956312417984009, 1.4980136156082153, 1.5423959493637085, 1.6264386177062988, 1.752126693725586, 1.846935510635376, 2.469531536102295, 1.622459053993225, 1.2726876735687256, 1.5585708618164062, 1.9870573282241821, 2.169248580932617, 1.6185038089752197, 1.3094803094863892, 2.1684281826019287, 0.9473098516464233, 2.0959055423736572, 1.2198997735977173, 1.6581573486328125, 1.3964229822158813, 1.3392335176467896, 1.948081612586975, 1.3351192474365234, 1.2224578857421875, 1.4484825134277344, 0.9051042199134827, 0.9532817006111145, 1.2497615814208984, 2.0260446071624756, 1.9693502187728882, 1.4448308944702148, 1.532451868057251, 1.7212274074554443, 1.481695532798767, 0.9293838143348694, 1.573059320449829, 1.273274302482605, 1.208749532699585, 1.6390496492385864, 2.3411800861358643, 1.7289228439331055, 1.722346305847168, 1.0649306774139404, 1.5146055221557617, 1.3869065046310425, 2.0925052165985107, 1.986876130104065, 2.3680343627929688, 0.8671036958694458, 1.7698290348052979, 2.306485652923584, 0.9996905326843262, 2.650780200958252, 1.6786282062530518, 2.3577613830566406, 1.362066626548767, 1.2867023944854736, 1.5882424116134644, 2.6610524654388428, 0.9792168140411377, 2.1175177097320557, 1.7629790306091309, 1.820918083190918, 1.4673582315444946, 1.3095239400863647, 1.0703649520874023, 2.1561365127563477, 1.8232805728912354, 1.9505447149276733, 1.1626451015472412, 1.6534981727600098, 1.7172743082046509, 1.1816065311431885, 2.0423641204833984, 0.9770594835281372, 1.927557349205017, 2.1514880657196045, 1.4756132364273071, 2.1981418132781982, 1.1372580528259277, 1.362912893295288, 1.917000412940979, 1.3538345098495483, 2.341341733932495, 0.6943092346191406, 1.417230248451233, 2.0134055614471436, 1.687813639640808, 1.5403470993041992, 2.013913631439209, 1.6711773872375488, 1.604325771331787, 2.4909448623657227, 2.095639944076538, 2.0771238803863525, 2.0614519119262695, 0.8494542241096497, 1.3390899896621704, 1.2476999759674072, 1.5459809303283691, 1.0774017572402954, 2.167445182800293, 1.1276838779449463, 2.193544626235962, 1.2043108940124512, 0.9767090678215027, 1.878462791442871, 1.9194304943084717, 2.097028970718384, 1.9952646493911743, 1.7022454738616943, 2.2300467491149902, 1.45211660861969, 1.6239553689956665, 2.175745964050293, 1.568200945854187, 1.8136000633239746, 1.9481945037841797, 1.956398606300354, 1.9869871139526367, 1.085774540901184, 1.1045700311660767, 1.1648883819580078, 2.2836999893188477, 1.6652929782867432, 2.3461718559265137, 1.509799599647522, 2.112718343734741, 1.3384387493133545, 1.3899264335632324, 1.2661103010177612, 1.7300537824630737, 1.5580974817276, 1.4366799592971802, 2.1527340412139893, 0.8565722703933716, 1.353740930557251, 1.6027857065200806, 1.6428565979003906, 1.833260416984558, 1.8240563869476318, 1.3603806495666504, 2.0377652645111084, 1.1376328468322754, 1.7790050506591797, 1.2276442050933838, 1.9451699256896973, 1.6273994445800781, 0.9899714589118958, 72.22076416015625, 125.98465728759766, 78.14714813232422, 40.946048736572266, 155.82208251953125, 132.91746520996094, 156.63238525390625, 131.49493408203125, 71.293701171875, 121.6288070678711, 106.17557525634766, 100.40054321289062, 68.92033386230469, 65.39278411865234, 35.61757278442383, 121.7830810546875, 122.83856964111328, 71.8648910522461, 204.2224884033203, 150.91510009765625, 89.41058349609375, 56.84084701538086, 68.94473266601562, 185.0516357421875, 98.43142700195312, 266.81298828125, 156.86964416503906, 128.581298828125, 104.84806060791016, 284.9654541015625, 39.25439453125, 50.25018310546875, 63.038700103759766, 101.2525863647461, 38.03601837158203, 287.96490478515625, 182.8516387939453, 61.262664794921875, 99.70417785644531, 103.02548217773438, 89.0726318359375, 48.39227294921875, 160.7865447998047, 43.8797607421875, 204.0241241455078, 44.0567626953125, 80.28244018554688, 192.9795684814453, 123.69467163085938, 52.139739990234375, 202.46487426757812, 63.9169807434082, 46.31521224975586, 26.34747314453125, 201.36624145507812, 30.225677490234375, 116.25402069091797, 211.3582000732422, 32.77032470703125, 121.36214447021484, 213.4608154296875, 65.97808074951172, 89.78569793701172, 115.29761505126953, 128.3863067626953, 68.76717376708984, 125.7410888671875, 211.21690368652344, 107.44420623779297, 28.676176071166992, 50.333251953125, 93.4136734008789, 213.8008575439453, 146.66542053222656, 49.43935775756836, 261.8845520019531, 114.877197265625, 97.52066802978516, 133.04486083984375, 135.8616180419922, 98.53820037841797, 199.3137969970703, 185.04251098632812, 29.87347412109375, 39.80013656616211, 111.345947265625, 102.16353607177734, 38.20672607421875, 116.38030242919922, 386.78033447265625, 157.25225830078125, 51.12813186645508, 34.894412994384766, 81.14022064208984, 58.23117446899414, 203.6630859375, 82.15974426269531, 87.09173583984375, 56.740535736083984, 77.79790496826172, 141.99354553222656, 35.548526763916016, 114.84735107421875, 146.7113037109375, 32.18860626220703, 113.96056365966797, 50.302059173583984, 134.0316162109375, 114.19215393066406, 64.6314468383789, 71.2423095703125, 109.44880676269531, 261.9148864746094, 83.38839721679688, 55.56600570678711, 70.54499053955078, 136.19281005859375, 25.641630172729492, 30.76007652282715, 60.57269287109375, 55.5689697265625, 53.49627685546875, 111.55844116210938, 126.92281341552734, 29.09814453125, 209.8653106689453, 91.31485748291016, 48.89704895019531, 172.77952575683594, 168.93673706054688, 63.31192398071289, 46.48992919921875, 127.55413818359375, 112.68856811523438, 27.400550842285156, 127.489013671875, 30.7442626953125, 49.259246826171875, 33.91731262207031, 32.11954116821289, 196.5306396484375, 114.60674285888672, 203.32286071777344, 65.91168975830078, 69.85883331298828, 127.77951049804688, 193.2147216796875, 91.24359130859375, 232.6923828125, 105.36238098144531, 164.6375732421875, 123.3027114868164, 84.01134490966797, 187.14089965820312, 264.91937255859375, 228.73497009277344, 31.0921630859375, 161.11691284179688, 106.329345703125, 85.68769073486328, 62.3333740234375, 91.2547836303711, 67.75518035888672, 84.69985961914062, 101.8589859008789, 54.88533020019531, 55.214080810546875, 117.53632354736328, 120.7077865600586, 31.32008171081543, 86.02689361572266, 29.97415542602539, 179.000732421875, 40.70123291015625, 99.6116943359375, 95.43949127197266, 111.61699676513672, 53.833740234375, 102.71739959716797, 188.3152618408203, 169.95420837402344, 45.779510498046875, 151.89505004882812, 233.447998046875, 33.57281494140625, 30.24560546875, 64.9670181274414, 32.59356689453125, 28.935009002685547, 56.74114227294922, 57.80562210083008, 33.9167594909668, 29.2799072265625, 64.37212371826172, 158.39344787597656, 84.4197998046875, 34.38715362548828, 64.41248321533203, 83.80950927734375, 127.40645599365234, 153.584716796875, 29.75313949584961, 165.4897003173828, 31.030467987060547, 27.221649169921875, 223.60281372070312, 132.05723571777344, 109.74853515625, 87.72184753417969, 38.15910339355469, 80.7908706665039, 94.53045654296875, 118.74243927001953, 94.70958709716797, 194.6708526611328, 141.84056091308594, 24.600189208984375, 107.75786590576172, 154.825439453125, 246.0707550048828, 47.01789093017578, 114.65133666992188, 129.60870361328125, 110.77259826660156, 126.9958267211914, 57.39004898071289, 39.4183349609375, 137.53038024902344, 101.9571304321289, 66.55305480957031, 218.7796630859375, 193.1649627685547, 60.220951080322266, 203.01426696777344, 31.800872802734375, 122.1264419555664, 175.5297088623047, 162.95758056640625, 77.37102508544922, 184.97817993164062, 116.24515533447266, 202.91046142578125, 357.98760986328125, 132.95159912109375, 151.2791748046875, 146.15753173828125, 78.57173919677734, 155.85964965820312, 52.630615234375, 34.2412109375, 50.072021484375, 43.769412994384766, 92.357666015625, 167.4835968017578, 24.799640655517578, 141.61007690429688, 214.1902313232422, 76.53269958496094, 99.852783203125, 94.77153778076172, 108.56110382080078, 127.14289093017578, 134.42849731445312, 310.6140441894531, 108.83135223388672, 122.19189453125, 180.1900177001953, 81.38900756835938, 68.52639770507812, 253.2152099609375, 23.587413787841797, 155.0494842529297, 141.6811065673828, 217.87890625, 53.76742935180664, 99.4032974243164, 136.07237243652344, 108.0531005859375, 287.0845947265625, 272.9927062988281, 46.52251434326172, 165.41046142578125, 180.08615112304688, 32.0715217590332, 85.097900390625, 53.08657455444336, 83.90625, 79.62977600097656, 304.7829895019531, 336.9752197265625, 175.89877319335938, 109.79621124267578, 102.95989990234375, 278.15740966796875, 65.78775787353516, 49.98616027832031, 180.87960815429688, 26.311737060546875, 207.264404296875, 67.12187957763672, 2.7094502449035645, 1.5156220197677612, 2.8594253063201904, 2.923992156982422, 2.4047389030456543, 3.0954906940460205, 3.1668713092803955, 3.4104321002960205, 3.3419125080108643, 2.40169620513916, 1.6314557790756226, 1.7442824840545654, 1.9658002853393555, 2.3328561782836914, 2.8147671222686768, 3.113032579421997, 1.9269722700119019, 3.304030656814575, 3.1505444049835205, 2.9142885208129883, 1.7454290390014648, 3.275590181350708, 1.650775671005249, 2.144108772277832, 2.5173513889312744, 1.4606488943099976, 2.5280332565307617, 2.9391772747039795, 2.6714160442352295, 2.9241058826446533, 1.5618261098861694, 1.961226463317871, 2.280649423599243, 2.9856669902801514, 2.5849690437316895, 2.8247814178466797, 1.2634897232055664, 2.1722846031188965, 1.63795006275177, 2.1830320358276367, 3.3179218769073486, 1.7567342519760132, 2.77569580078125, 2.434659242630005, 3.5989294052124023, 2.3860902786254883, 1.5425100326538086, 1.5439502000808716, 2.5654492378234863, 1.6260061264038086, 2.435382127761841, 3.1749637126922607, 2.1397132873535156, 1.8718175888061523, 1.7182015180587769, 1.6390584707260132, 3.2230632305145264, 3.9357681274414062, 1.2480218410491943, 2.3199291229248047, 2.0363168716430664, 2.4895694255828857, 2.575545072555542, 2.3309552669525146, 2.7612340450286865, 2.6689391136169434, 1.410367727279663, 1.5057542324066162, 2.8698513507843018, 3.4751102924346924, 2.28855037689209, 3.6133439540863037, 1.2949588298797607, 2.1120002269744873, 1.7997198104858398, 2.87081241607666, 2.849353075027466, 2.8647491931915283, 1.5895053148269653, 2.5272226333618164, 2.883647918701172, 3.573289155960083, 2.2369489669799805, 3.364596366882324, 1.1372488737106323, 3.364384889602661, 2.2704896926879883, 2.2540595531463623, 2.620013475418091, 2.363713264465332, 1.3305974006652832, 1.7771025896072388, 2.079373359680176, 3.07894229888916, 1.8177539110183716, 1.852644920349121, 2.0694384574890137, 2.0049009323120117, 1.7392503023147583, 2.6607556343078613, 2.724536180496216, 2.035689353942871, 2.3059561252593994, 1.6445626020431519, 2.4524965286254883, 2.7076544761657715, 1.9892245531082153, 2.777923583984375, 2.2879908084869385, 3.32719349861145, 3.2744626998901367, 3.081608295440674, 3.549358367919922, 2.032567024230957, 3.2734310626983643, 2.635251045227051, 3.3060929775238037, 3.1012489795684814, 2.559908866882324, 2.041707754135132, 3.080498695373535, 3.3976409435272217, 1.2730536460876465, 4.034587860107422, 2.7036964893341064, 1.62757408618927, 3.1691415309906006, 3.3305163383483887, 1.9813894033432007, 3.3360061645507812, 3.682133913040161, 2.8650360107421875, 2.4784579277038574, 2.451632261276245, 2.496384620666504, 2.251704454421997, 3.030341148376465, 2.5261905193328857, 2.0189027786254883, 2.559730052947998, 2.628843069076538, 2.9333324432373047, 2.879276752471924, 1.3978948593139648, 2.6596155166625977, 2.9614720344543457, 2.6634597778320312, 2.366900682449341, 3.419872999191284, 2.0239617824554443, 1.9213870763778687, 2.4944732189178467, 3.113755464553833, 2.2863245010375977, 2.9027698040008545, 2.3398983478546143, 2.283745765686035, 1.6730971336364746, 2.0206804275512695, 2.139033555984497, 2.703692674636841, 2.09378719329834, 1.8113231658935547, 2.067629814147949, 2.0271568298339844, 2.709115505218506, 3.307774782180786, 2.567309617996216, 3.599961519241333, 3.5286946296691895, 2.495572090148926, 3.2275140285491943, 3.062119722366333, 2.804885149002075, 1.2958992719650269, 1.946380853652954, 3.1703426837921143, 2.352548837661743, 1.894123911857605, 2.849799394607544, 2.3014323711395264, 1.7943071126937866, 3.1643779277801514, 3.3942718505859375, 1.7789030075073242, 2.148909568786621, 2.412134885787964, 3.241190195083618, 2.349961280822754, 2.5383245944976807, 2.1999311447143555, 3.4963061809539795, 2.7219765186309814, 3.3933489322662354, 2.387070655822754, 2.876939058303833, 2.7026665210723877, 2.0031769275665283, 3.134777069091797, 1.9529097080230713, 2.2778666019439697, 1.4705246686935425, 1.26872718334198, 2.3923518657684326, 1.7606326341629028, 2.3661584854125977, 2.9798784255981445, 2.245513916015625, 2.686570405960083, 3.4464683532714844, 2.521662950515747, 3.545260429382324, 2.0403010845184326, 2.637974739074707, 3.2459611892700195, 1.9799867868423462, 2.8992412090301514, 1.4450759887695312, 2.936697244644165, 2.8176350593566895, 1.935038447380066, 2.225691795349121, 2.792344808578491, 2.0400772094726562, 2.3428456783294678, 3.9682230949401855, 2.6873114109039307, 3.6849467754364014, 1.4308438301086426, 1.7798147201538086, 2.4106149673461914, 1.565852165222168, 2.3241074085235596, 2.513456106185913, 1.9550046920776367, 2.992852210998535, 3.312028169631958, 2.7296533584594727, 2.1633858680725098, 1.3587104082107544, 2.3833231925964355, 2.880720376968384, 3.286465883255005, 2.706956148147583, 2.8469254970550537, 2.7161052227020264, 1.9834160804748535, 2.4400265216827393, 1.9368948936462402, 2.7591753005981445, 2.907109260559082, 1.750544548034668, 1.2746819257736206, 2.614724636077881, 2.488992929458618, 1.805521845817566, 2.839752674102783, 2.058424711227417, 2.20345401763916, 3.539215087890625, 1.670898675918579, 2.3974294662475586, 1.8881462812423706, 2.150378465652466, 2.6872894763946533, 3.853074312210083, 2.178219795227051, 2.1942052841186523, 1.8310478925704956, 3.7398643493652344, 2.4432389736175537, 2.9137213230133057, 2.1380600929260254, 2.5000741481781006, 3.5190837383270264, 2.456191062927246, 2.981806516647339, 3.041088104248047, 3.302199602127075, 1.9424484968185425, 1.604756474494934, 1.9119923114776611, 2.0858702659606934, 2.2056798934936523, 1.876710295677185, 2.4548823833465576, 1.430550456047058, 2.0414438247680664, 2.4267690181732178, 1.4798328876495361, 1.5547045469284058, 2.5667755603790283, 1.2054595947265625, 3.0996205806732178, 2.498699426651001, 3.02793025970459, 2.382840871810913, 3.215843439102173, 4.102165222167969, 3.405226945877075, 0.23157286643981934, 0.16270224750041962, 0.1718991994857788, 0.16308331489562988, 0.22995389997959137, 0.14479918777942657, 0.23311832547187805, 0.12828779220581055, 0.1667734831571579, 0.14143836498260498, 0.23786212503910065, 0.1236191913485527, 0.1794356107711792, 0.15581351518630981, 0.16559669375419617, 0.24780185520648956, 0.15920457243919373, 0.1873181164264679, 0.2164212167263031, 0.18156763911247253, 0.1773604154586792, 0.16804003715515137, 0.2059018462896347, 0.1497289389371872, 0.13630610704421997, 0.23650209605693817, 0.15518659353256226, 0.14591309428215027, 0.17958056926727295, 0.14479881525039673, 0.15739275515079498, 0.18248872458934784, 0.16625003516674042, 0.2010432779788971, 0.23351582884788513, 0.13914427161216736, 0.15724463760852814, 0.22167518734931946, 0.09894705563783646, 0.20978304743766785, 0.189558744430542, 0.17652663588523865, 0.18586057424545288, 0.19832061231136322, 0.10122880339622498, 0.24263063073158264, 0.12307548522949219, 0.24920082092285156, 0.1493697464466095, 0.18351677060127258, 0.14108802378177643, 0.25880423188209534, 0.1634039580821991, 0.16376182436943054, 0.1786128133535385, 0.25501906871795654, 0.15678954124450684, 0.3096478283405304, 0.17940405011177063, 0.15524472296237946, 0.14534606039524078, 0.25349727272987366, 0.21157769858837128, 0.1754150390625, 0.2986118495464325, 0.16936977207660675, 0.18259873986244202, 0.15598905086517334, 0.19837231934070587, 0.13110865652561188, 0.15038739144802094, 0.14852285385131836, 0.2005508691072464, 0.25756052136421204, 0.1835445612668991, 0.13104015588760376, 0.1206568032503128, 0.18093636631965637, 0.1350805014371872, 0.15979966521263123, 0.12504301965236664, 0.19334746897220612, 0.1913479119539261, 0.19792215526103973, 0.14159995317459106, 0.16263893246650696, 0.24392090737819672, 0.15951813757419586, 0.17003756761550903, 0.1813594549894333, 0.2057616114616394, 0.1950325220823288, 0.133808895945549, 0.2675214111804962, 0.14032025635242462, 0.21142013370990753, 0.2073107808828354, 0.14437831938266754, 0.1797819882631302, 0.13738951086997986, 0.1662781834602356, 0.1888185441493988, 0.20559869706630707, 0.13129495084285736, 0.18689696490764618, 0.1658211499452591, 0.15182429552078247, 0.18761637806892395, 0.1950596123933792, 0.2180696278810501, 0.17700563371181488, 0.11975892633199692, 0.17505677044391632, 0.12862713634967804, 0.2255978286266327, 0.12359318137168884, 0.17677633464336395, 0.2303839474916458, 0.12284456938505173, 0.2519700229167938, 0.1476801633834839, 0.18260738253593445, 0.143100768327713, 0.17930816113948822, 0.21358554065227509, 0.1651810109615326, 0.16893120110034943, 0.17114165425300598, 0.13448846340179443, 0.18337905406951904, 0.12988266348838806, 0.15745335817337036, 0.2551834285259247, 0.16715961694717407, 0.2637801170349121, 0.1586935967206955, 0.18760429322719574, 0.21183016896247864, 0.25109612941741943, 0.18632175028324127, 0.1632559597492218, 0.189488485455513, 0.16698184609413147, 0.2109818160533905, 0.1423993706703186, 0.17973792552947998, 0.11776403337717056, 0.18332335352897644, 0.19580626487731934, 0.21232779324054718, 0.17423565685749054, 0.2179839015007019, 0.1456754505634308, 0.1915513128042221, 0.14223983883857727, 0.19445495307445526, 0.22114291787147522, 0.16328300535678864, 0.1728304624557495, 0.1703866422176361, 0.2654590606689453, 0.20891867578029633, 0.1402212232351303, 0.18003962934017181, 0.14761538803577423, 0.21322239935398102, 0.16886916756629944, 0.14494524896144867, 0.185620978474617, 0.16196714341640472, 0.17011713981628418, 0.20581825077533722, 0.18704183399677277, 0.18087151646614075, 0.24130257964134216, 0.17187638580799103, 0.25919196009635925, 0.20003634691238403, 0.23272208869457245, 0.17214594781398773, 0.17850027978420258, 0.19360598921775818, 0.10711387544870377, 0.2259330451488495, 0.12389347702264786, 0.18732905387878418, 0.20787490904331207, 0.18967145681381226, 0.0848691537976265, 0.220722496509552, 0.14036887884140015, 0.22233809530735016, 0.10957913845777512, 0.19913840293884277, 0.2632271647453308, 0.14101819694042206, 0.17226335406303406, 0.1477949321269989, 0.17090220749378204, 0.22717714309692383, 0.15015143156051636, 0.16913306713104248, 0.21042746305465698, 0.21483942866325378, 0.22800688445568085, 0.16373255848884583, 0.13432760536670685, 0.1657993346452713, 0.2123083621263504, 0.27235355973243713, 0.22845737636089325, 0.14360442757606506, 0.14890314638614655, 0.23587530851364136, 0.12519942224025726, 0.14711813628673553, 0.16541698575019836, 0.14457552134990692, 0.2071092426776886, 0.19222593307495117, 0.20827969908714294, 0.17565396428108215, 0.14995208382606506, 0.18793782591819763, 0.16478385031223297, 0.12365350127220154, 0.1531747430562973, 0.21316619217395782, 0.22604449093341827, 0.15594661235809326, 0.1848156750202179, 0.19985778629779816, 0.11475646495819092, 0.16863404214382172, 0.278651624917984, 0.22314126789569855, 0.18684864044189453, 0.22824664413928986, 0.12232382595539093, 0.2388918250799179, 0.16728579998016357, 0.2559657394886017, 0.22303447127342224, 0.19968238472938538, 0.1815904974937439, 0.16636452078819275, 0.19400493800640106, 0.17375755310058594, 0.12086160480976105, 0.17767095565795898, 0.14615687727928162, 0.13725635409355164, 0.17012202739715576, 0.15106436610221863, 0.19601836800575256, 0.1396327018737793, 0.140568807721138, 0.16853386163711548, 0.23424990475177765, 0.10364372283220291, 0.20024125277996063, 0.19905146956443787, 0.20553988218307495, 0.11024204641580582, 0.2658664286136627, 0.18280215561389923, 0.17043468356132507, 0.2293754667043686, 0.17109782993793488, 0.21998317539691925, 0.20076537132263184, 0.13804301619529724, 0.232212096452713, 0.18115508556365967, 0.21692442893981934, 0.19598428905010223, 0.16830584406852722, 0.15653592348098755, 0.13539022207260132, 0.19224391877651215, 0.0993591845035553, 0.19481642544269562, 0.16377975046634674, 0.10527288168668747, 0.19812946021556854, 0.19497792422771454, 0.18184620141983032, 0.1331218183040619, 0.204764261841774, 0.24475066363811493, 0.16682469844818115, 0.16854800283908844, 0.22764331102371216, 0.12878063321113586, 0.2510664761066437, 0.20862311124801636, 0.13208074867725372, 0.19189265370368958, 0.18852196633815765, 0.1448550820350647, 1.5706018209457397, 1.148164987564087, 1.2274445295333862, 1.911497712135315, 1.5165427923202515, 2.2648658752441406, 1.280480146408081, 1.592612862586975, 1.2224352359771729, 1.9446220397949219, 1.6659847497940063, 1.2192792892456055, 1.7396700382232666, 1.9637788534164429, 1.4607043266296387, 1.6440023183822632, 1.5401253700256348, 1.7203359603881836, 1.1702768802642822, 2.0404467582702637, 2.4053573608398438, 1.3357511758804321, 0.8825135827064514, 1.320273756980896, 1.4599279165267944, 1.7572866678237915, 1.4161736965179443, 1.9608761072158813, 1.4373804330825806, 1.992151141166687, 2.2068867683410645, 1.3341271877288818, 1.585526704788208, 1.5970652103424072, 1.2659882307052612, 1.6276239156723022, 1.7210651636123657, 2.256401538848877, 1.9790902137756348, 1.3511478900909424, 1.279197096824646, 2.159135341644287, 1.0840215682983398, 1.6883312463760376, 1.7553939819335938, 1.3464454412460327, 0.936255931854248, 1.8286653757095337, 1.3757416009902954, 1.7116349935531616, 1.5957832336425781, 2.6995208263397217, 1.371698260307312, 1.8947956562042236, 1.9986011981964111, 1.7786110639572144, 1.3280041217803955, 1.4801123142242432, 2.370917558670044, 0.9101629257202148, 1.6129698753356934, 1.2609875202178955, 1.1060757637023926, 0.6957837343215942, 1.9875520467758179, 2.1787710189819336, 1.098351240158081, 1.4001140594482422, 1.331953763961792, 1.6432151794433594, 1.9968258142471313, 1.9217346906661987, 1.5156826972961426, 1.1065765619277954, 1.0269287824630737, 1.2389624118804932, 1.0270130634307861, 1.6980853080749512, 1.6695772409439087, 1.0571107864379883, 1.2625576257705688, 1.0231146812438965, 2.9433224201202393, 2.0710883140563965, 1.5294849872589111, 2.261701822280884, 1.1266884803771973, 1.7493761777877808, 1.2655612230300903, 1.2512261867523193, 0.916102409362793, 1.5986196994781494, 1.9868720769882202, 1.7432833909988403, 1.462601900100708, 2.1102914810180664, 1.0444462299346924, 1.3243576288223267, 1.0048258304595947, 1.178762435913086, 0.8788335919380188, 1.7506815195083618, 1.2201368808746338, 2.061382293701172, 2.1847269535064697, 2.19771671295166, 1.3587801456451416, 1.7106279134750366, 2.6185333728790283, 1.8502088785171509, 2.107402801513672, 1.0577316284179688, 2.0406253337860107, 1.168121099472046, 1.4466664791107178, 1.285757064819336, 1.3822062015533447, 1.5558785200119019, 1.7675516605377197, 1.0318922996520996, 1.207574486732483, 1.412498116493225, 1.1709755659103394, 1.6155108213424683, 2.1356687545776367, 0.9697747826576233, 1.8642698526382446, 1.9152873754501343, 1.7339696884155273, 0.7824848294258118, 1.0158478021621704, 1.3706547021865845, 1.5001909732818604, 1.494158148765564, 1.682367205619812, 1.925923466682434, 2.301140308380127, 1.1569664478302002, 1.3063591718673706, 1.3081105947494507, 1.9059536457061768, 1.4781854152679443, 1.0626368522644043, 1.2606767416000366, 1.2803372144699097, 2.0022706985473633, 1.720125675201416, 1.5967527627944946, 1.8864693641662598, 2.2832963466644287, 1.3069854974746704, 1.031209111213684, 1.378928780555725, 1.0563935041427612, 1.264009952545166, 1.1887481212615967, 1.6817289590835571, 1.6798365116119385, 1.2630912065505981, 1.4927210807800293, 2.1047720909118652, 1.218886375427246, 2.362478017807007, 2.015092611312866, 1.3775056600570679, 1.512559175491333, 1.2860829830169678, 1.2663685083389282, 1.7357887029647827, 1.1935601234436035, 1.223626732826233, 1.128758192062378, 1.6042410135269165, 1.662475824356079, 1.6107195615768433, 1.2521904706954956, 1.4470325708389282, 1.172670602798462, 2.0138440132141113, 1.066828727722168, 1.893951654434204, 2.480618715286255, 1.602789282798767, 1.977089524269104, 1.7765820026397705, 1.8760600090026855, 1.8384819030761719, 1.5004802942276, 1.5263582468032837, 1.2059894800186157, 2.2644336223602295, 1.300495982170105, 1.3851791620254517, 1.2672268152236938, 1.5376592874526978, 1.091138482093811, 1.6012428998947144, 1.4601141214370728, 1.622020959854126, 1.6558358669281006, 2.179382562637329, 1.467121958732605, 1.6492550373077393, 1.447546362876892, 1.158110499382019, 1.5143038034439087, 2.1823630332946777, 1.486389398574829, 1.837738275527954, 1.2437264919281006, 1.6950544118881226, 1.893657922744751, 1.7641985416412354, 1.7614611387252808, 1.0060120820999146, 1.4820505380630493, 1.5085105895996094, 1.9257782697677612, 1.8972424268722534, 2.159444808959961, 1.2769638299942017, 1.7149804830551147, 1.9728745222091675, 1.4592554569244385, 1.5974769592285156, 1.3611892461776733, 1.3243402242660522, 1.7165573835372925, 1.1698179244995117, 1.7174102067947388, 2.3334169387817383, 1.4234215021133423, 0.9669545292854309, 1.667938232421875, 1.602367877960205, 1.0751979351043701, 2.0030195713043213, 1.994340181350708, 1.9156811237335205, 1.7233631610870361, 1.2983529567718506, 2.3832919597625732, 1.5467232465744019, 1.7469921112060547, 2.519500732421875, 2.574265480041504, 1.4214632511138916, 1.5763589143753052, 1.8583968877792358, 1.4863226413726807, 2.5844452381134033, 2.103785991668701, 1.6827911138534546, 2.329101324081421, 1.2636967897415161, 1.5919564962387085, 1.0563887357711792, 1.200727939605713, 1.0778616666793823, 1.2011072635650635, 1.8338390588760376, 1.9358822107315063, 2.2548351287841797, 1.794327974319458, 1.5012651681900024, 2.2723212242126465, 1.6590641736984253, 1.345388412475586, 1.6185429096221924, 1.5879653692245483, 2.061434268951416, 2.373136043548584, 2.4568257331848145, 1.7720881700515747, 1.920468807220459, 1.7577645778656006, 1.3291600942611694, 1.5256164073944092, 1.8331718444824219, 1.7766516208648682, 1.1230762004852295, 0.9564324617385864, 1.721387267112732, 0.7292459011077881, 2.2347664833068848, 1.3043149709701538, 1.3015512228012085, 1.4907253980636597, 2.0471079349517822, 1.5002473592758179, 0.8527576923370361, 1.5357805490493774, 1.3354629278182983, 1.58904230594635, 1.2285414934158325, 0.9895954132080078, 1.5628174543380737, 2.129624843597412, 1.1403353214263916, 1.6973565816879272, 155.35006713867188, 192.9934844970703, 121.815185546875, 150.19859313964844, 69.63956451416016, 124.1893310546875, 92.49017333984375, 38.13714599609375, 284.0123291015625, 106.1786117553711, 154.5687713623047, 202.6707763671875, 213.4793701171875, 83.28638458251953, 44.847957611083984, 145.635498046875, 202.1712646484375, 89.3250732421875, 37.7860107421875, 51.4183349609375, 119.02159881591797, 189.9220733642578, 54.63128662109375, 372.1039733886719, 172.4638671875, 45.72108840942383, 36.96101760864258, 35.03969192504883, 204.321044921875, 34.677947998046875, 249.0137481689453, 69.33185577392578, 98.77330017089844, 65.52275848388672, 30.12013053894043, 210.9720458984375, 68.62773895263672, 45.15424346923828, 32.9039306640625, 154.24472045898438, 55.875244140625, 70.9808349609375, 52.74394226074219, 109.12609100341797, 76.31060028076172, 46.555908203125, 54.78446578979492, 135.7113037109375, 208.99755859375, 31.32977294921875, 137.69876098632812, 24.77582550048828, 30.136810302734375, 159.5732421875, 123.80177307128906, 267.96343994140625, 83.85398864746094, 36.644744873046875, 96.55291748046875, 379.6136779785156, 114.54354858398438, 109.72438049316406, 23.85498046875, 62.09724044799805, 34.514312744140625, 96.3311538696289, 356.09869384765625, 74.06051635742188, 30.481876373291016, 62.01118850708008, 31.583866119384766, 53.71932601928711, 99.48856353759766, 66.0816650390625, 205.94699096679688, 141.3524932861328, 225.33621215820312, 32.23583984375, 220.7749786376953, 196.78379821777344, 191.9896697998047, 163.9590606689453, 124.42495727539062, 157.595458984375, 37.78894805908203, 138.7325439453125, 79.08258819580078, 123.23202514648438, 33.5787353515625, 30.95060920715332, 62.70074462890625, 151.69345092773438, 42.945858001708984, 136.62744140625, 252.97052001953125, 67.7345962524414, 115.12612915039062, 51.87253952026367, 162.73399353027344, 146.89825439453125, 110.63954162597656, 146.6988067626953, 73.29371643066406, 131.12823486328125, 127.2122802734375, 232.8266143798828, 25.35223388671875, 143.19464111328125, 102.03763580322266, 37.84903335571289, 166.70608520507812, 118.33760833740234, 97.50907135009766, 39.39278030395508, 218.2549591064453, 154.79859924316406, 37.88503646850586, 55.70400619506836, 54.91375732421875, 100.60871124267578, 364.09991455078125, 165.56277465820312, 38.0516357421875, 308.73565673828125, 138.3607940673828, 83.70571899414062, 205.2430419921875, 32.41094970703125, 68.98635864257812, 131.70335388183594, 55.9912109375, 71.05657958984375, 131.1756134033203, 163.03640747070312, 62.62970733642578, 158.72084045410156, 46.40380859375, 37.23056411743164, 251.01046752929688, 141.947265625, 111.71300506591797, 37.92132568359375, 164.1338653564453, 67.38964080810547, 320.7008056640625, 250.2879638671875, 138.03753662109375, 52.87936782836914, 375.669921875, 79.80381774902344, 285.7411193847656, 85.5887680053711, 41.939754486083984, 231.34092712402344, 161.98171997070312, 166.14984130859375, 103.1205062866211, 115.14437103271484, 98.91558074951172, 112.9072265625, 167.31761169433594, 121.61077880859375, 145.37364196777344, 110.8739242553711, 119.63201904296875, 96.2420883178711, 21.9368896484375, 130.49363708496094, 127.36141967773438, 191.72251892089844, 47.7508430480957, 39.92453384399414, 74.6224136352539, 30.953216552734375, 169.9370880126953, 103.95157623291016, 34.269039154052734, 35.59434127807617, 57.53987121582031, 125.5476303100586, 164.32455444335938, 105.55926513671875, 50.424617767333984, 67.36273193359375, 75.17682647705078, 185.48974609375, 63.312469482421875, 59.35931396484375, 261.66754150390625, 235.7235565185547, 136.3994140625, 179.4178466796875, 47.51171875, 264.431396484375, 109.39324951171875, 248.52113342285156, 42.54419708251953, 95.66117095947266, 43.48162841796875, 145.53982543945312, 70.64340209960938, 119.84602355957031, 18.027807235717773, 32.78367233276367, 39.14113998413086, 44.62298583984375, 168.7860565185547, 77.052734375, 189.54150390625, 68.73406982421875, 153.34971618652344, 62.5822639465332, 162.41546630859375, 164.43505859375, 99.07955169677734, 56.176239013671875, 81.5626220703125, 90.85454559326172, 266.1784973144531, 83.24539184570312, 181.98681640625, 32.050865173339844, 77.63714599609375, 226.2801513671875, 250.8070068359375, 24.800703048706055, 20.33428955078125, 117.502197265625, 106.6895980834961, 228.97216796875, 22.152034759521484, 110.15863800048828, 130.16552734375, 32.524906158447266, 124.73519134521484, 56.546146392822266, 128.21295166015625, 30.970947265625, 234.431640625, 97.72612762451172, 230.1625213623047, 130.68096923828125, 223.21495056152344, 85.0999755859375, 124.0836410522461, 133.01905822753906, 112.00939178466797, 138.71112060546875, 56.1881103515625, 26.503793716430664, 169.23060607910156, 245.972900390625, 224.8323974609375, 161.71205139160156, 38.56727600097656, 155.18096923828125, 75.41314697265625, 65.06683349609375, 25.841468811035156, 210.54356384277344, 212.8903045654297, 142.135009765625, 48.25193405151367, 33.4061279296875, 134.25537109375, 100.0831069946289, 45.96353530883789, 259.380615234375, 197.7412109375, 109.158447265625, 117.61112213134766, 31.9859619140625, 192.65478515625, 85.1336669921875, 122.54115295410156, 85.61076354980469, 123.12772369384766, 193.0099639892578, 98.949462890625, 247.084228515625, 96.32283020019531, 111.8402099609375, 118.82378387451172, 158.59967041015625, 60.88348388671875, 87.942138671875, 51.24725341796875, 85.54095458984375, 168.0585479736328, 156.92703247070312, 212.15676879882812, 33.92621994018555, 64.79705810546875, 48.24089813232422, 101.8840103149414, 202.34228515625, 160.8622283935547, 47.9400634765625, 175.35784912109375, 29.92840576171875, 2.8973283767700195, 2.744832754135132, 1.5736985206604004, 3.740046977996826, 3.425320863723755, 3.4761626720428467, 1.328713297843933, 3.1773126125335693, 3.043902635574341, 2.369093179702759, 1.9748411178588867, 1.8940670490264893, 2.0773138999938965, 1.8831875324249268, 2.548502206802368, 2.194075584411621, 2.423293352127075, 3.813366651535034, 1.7072384357452393, 2.906146764755249, 1.886210560798645, 1.8841179609298706, 3.743366003036499, 2.3974788188934326, 2.5407321453094482, 1.9481133222579956, 2.6239492893218994, 3.512467861175537, 1.1846760511398315, 2.715745210647583, 2.7971086502075195, 2.3713772296905518, 2.4566173553466797, 1.9156256914138794, 1.2855186462402344, 2.5667223930358887, 1.9598119258880615, 2.7377407550811768, 2.6468942165374756, 3.432438850402832, 3.219882011413574, 2.324324369430542, 1.9035292863845825, 3.262166738510132, 2.801215171813965, 3.140460252761841, 2.048914909362793, 3.5587098598480225, 3.1815996170043945, 3.3083529472351074, 1.6009321212768555, 1.7640180587768555, 1.4852280616760254, 1.5810410976409912, 3.4278414249420166, 2.048748016357422, 1.5769681930541992, 3.7375330924987793, 1.5882776975631714, 2.8970634937286377, 3.2581663131713867, 1.915919303894043, 2.9382481575012207, 1.6787551641464233, 2.3756608963012695, 1.797382116317749, 2.4127707481384277, 1.9316598176956177, 2.1440954208374023, 2.5015952587127686, 2.2541654109954834, 1.977225661277771, 3.1208832263946533, 2.3818960189819336, 3.5696935653686523, 1.7774544954299927, 1.105751872062683, 2.9684672355651855, 3.275895357131958, 2.4126410484313965, 1.796412467956543, 2.008561134338379, 2.5669212341308594, 1.9004524946212769, 2.5132455825805664, 3.375138521194458, 2.0511608123779297, 1.076926350593567, 3.022710084915161, 1.8457579612731934, 1.8195953369140625, 2.5329086780548096, 1.66087806224823, 1.9219573736190796, 1.4100370407104492, 1.3640536069869995, 3.345471143722534, 2.178896903991699, 2.834467649459839, 2.8357532024383545, 2.557110548019409, 1.527962327003479, 2.199970006942749, 1.6451549530029297, 2.232663154602051, 1.6429111957550049, 1.86491858959198, 2.0910072326660156, 2.287829637527466, 3.1547024250030518, 2.216154098510742, 2.0937814712524414, 3.0870277881622314, 1.419447898864746, 1.8607816696166992, 2.5627641677856445, 3.177297353744507, 1.9613943099975586, 1.7985305786132812, 3.4279754161834717, 3.0764360427856445, 2.018130302429199, 2.8446381092071533, 3.206601142883301, 1.3100603818893433, 2.5533392429351807, 2.705867052078247, 2.9154295921325684, 2.2242536544799805, 2.267247200012207, 1.8283147811889648, 3.8216564655303955, 1.306483268737793, 3.470160484313965, 1.8749504089355469, 1.2617125511169434, 2.7723135948181152, 2.4945569038391113, 2.3573966026306152, 3.1935532093048096, 1.9285296201705933, 2.2174596786499023, 2.1554365158081055, 3.01332950592041, 1.8645685911178589, 2.9761526584625244, 1.9372261762619019, 1.3012276887893677, 1.9325319528579712, 2.8756799697875977, 2.572880744934082, 1.8454465866088867, 2.150916337966919, 3.1459152698516846, 2.7858095169067383, 2.62957763671875, 1.8441953659057617, 3.006577730178833, 1.8300907611846924, 2.4641857147216797, 2.3434152603149414, 2.2919371128082275, 1.3327168226242065, 1.97642982006073, 2.462456703186035, 1.8153847455978394, 1.890380859375, 1.7910453081130981, 1.8906364440917969, 2.5471224784851074, 3.2781360149383545, 2.7472565174102783, 3.2740516662597656, 2.558333158493042, 2.5408809185028076, 1.8861206769943237, 2.370549440383911, 3.4140636920928955, 1.8613635301589966, 2.8656342029571533, 2.8484508991241455, 1.6997054815292358, 2.4332356452941895, 2.127161741256714, 2.32727313041687, 2.9807546138763428, 1.812538743019104, 3.5759172439575195, 2.3534770011901855, 1.708659052848816, 1.4674955606460571, 1.8167448043823242, 1.803939938545227, 2.930211067199707, 2.693906307220459, 2.8536462783813477, 1.7569488286972046, 3.1266627311706543, 1.8383512496948242, 2.6736481189727783, 1.7377642393112183, 2.4372127056121826, 2.448737144470215, 2.0821309089660645, 4.315422058105469, 1.8358526229858398, 3.295962333679199, 2.5896008014678955, 2.9234683513641357, 3.032230854034424, 3.063804864883423, 2.9464833736419678, 2.0905275344848633, 3.1853768825531006, 2.5362749099731445, 1.571486473083496, 2.1839637756347656, 1.6916604042053223, 2.70920467376709, 2.609088182449341, 3.1185107231140137, 2.8405139446258545, 2.7724437713623047, 3.06033992767334, 3.606806516647339, 2.4548768997192383, 2.824474334716797, 2.0280559062957764, 1.732981562614441, 2.121411085128784, 1.8959746360778809, 1.5320687294006348, 3.377326250076294, 2.159975528717041, 2.1112422943115234, 1.9966896772384644, 2.520270586013794, 1.4876213073730469, 2.821444034576416, 3.494466543197632, 3.522688627243042, 1.977413296699524, 2.328467607498169, 2.8201451301574707, 2.5555877685546875, 3.0217926502227783, 2.919552803039551, 2.2225546836853027, 1.9032049179077148, 2.746920347213745, 2.903092622756958, 1.6937599182128906, 2.0351669788360596, 1.1777304410934448, 2.1939268112182617, 2.247096061706543, 2.7735226154327393, 3.021085739135742, 3.305691957473755, 1.807045817375183, 2.4411473274230957, 2.2417235374450684, 1.7394057512283325, 2.8778045177459717, 2.7372350692749023, 2.349473714828491, 2.875725746154785, 1.634333610534668, 2.8739569187164307, 1.9561834335327148, 2.2018022537231445, 2.7803280353546143, 1.7595757246017456, 2.6673009395599365, 1.9617797136306763, 2.092731475830078, 2.5646698474884033, 1.1717537641525269, 2.885075569152832, 1.8421659469604492, 2.9537675380706787, 2.5753719806671143, 3.255744218826294, 1.6658978462219238, 2.786961555480957, 2.7013580799102783, 1.512293815612793, 2.2638463973999023, 1.359233021736145, 2.2016656398773193, 2.7938296794891357, 2.133044719696045, 3.963870048522949, 2.765254497528076, 1.923319935798645, 2.436474323272705, 3.306288719177246, 2.4472055435180664, 3.7182536125183105, 2.1394529342651367, 0.15709760785102844, 0.13558243215084076, 0.14437885582447052, 0.07971946895122528, 0.21986892819404602, 0.16502681374549866, 0.20158782601356506, 0.17267577350139618, 0.19136998057365417, 0.16822974383831024, 0.17199748754501343, 0.25047874450683594, 0.17617255449295044, 0.12114596366882324, 0.20805615186691284, 0.15712696313858032, 0.15137355029582977, 0.19163735210895538, 0.20738369226455688, 0.10112140327692032, 0.2048930674791336, 0.25543537735939026, 0.20269286632537842, 0.14913541078567505, 0.20031026005744934, 0.16856268048286438, 0.3035796880722046, 0.22146642208099365, 0.24280810356140137, 0.16759498417377472, 0.14328721165657043, 0.17857973277568817, 0.1401347666978836, 0.18505004048347473, 0.12585698068141937, 0.10463251918554306, 0.19456897675991058, 0.19055965542793274, 0.23611342906951904, 0.2388898730278015, 0.17014829814434052, 0.20606490969657898, 0.15327602624893188, 0.15891610085964203, 0.1600717157125473, 0.21114036440849304, 0.24845688045024872, 0.2025495320558548, 0.17556770145893097, 0.1744808852672577, 0.1770642101764679, 0.18842950463294983, 0.17121757566928864, 0.20408481359481812, 0.2361185997724533, 0.13595379889011383, 0.2140483409166336, 0.13693054020404816, 0.1734279841184616, 0.19490712881088257, 0.20523665845394135, 0.15389972925186157, 0.1435377597808838, 0.22840236127376556, 0.2670735716819763, 0.09131818264722824, 0.1539566069841385, 0.21563339233398438, 0.21063929796218872, 0.18409405648708344, 0.21098849177360535, 0.22267794609069824, 0.15964080393314362, 0.2157829999923706, 0.2603292465209961, 0.2395762950181961, 0.16778530180454254, 0.15622974932193756, 0.19385555386543274, 0.16973422467708588, 0.20889803767204285, 0.19410474598407745, 0.2426486760377884, 0.2339925765991211, 0.21344397962093353, 0.1927778273820877, 0.16462436318397522, 0.1574838012456894, 0.16707460582256317, 0.22367385029792786, 0.1482701301574707, 0.21874894201755524, 0.11070624738931656, 0.1612687110900879, 0.1730436533689499, 0.21334518492221832, 0.21311073005199432, 0.12469728291034698, 0.13052265346050262, 0.2378987818956375, 0.21347877383232117, 0.20249716937541962, 0.2022499442100525, 0.18826302886009216, 0.19796817004680634, 0.23732423782348633, 0.16395995020866394, 0.23815584182739258, 0.21364420652389526, 0.14502273499965668, 0.23689454793930054, 0.18345366418361664, 0.1859242022037506, 0.20918597280979156, 0.14149309694766998, 0.11218912899494171, 0.1449662297964096, 0.17602957785129547, 0.1732756793498993, 0.20278429985046387, 0.1540769785642624, 0.18695123493671417, 0.139163076877594, 0.2148718237876892, 0.13938575983047485, 0.28015586733818054, 0.26184675097465515, 0.13742589950561523, 0.1461516171693802, 0.1790899634361267, 0.14121508598327637, 0.2155778855085373, 0.1413680911064148, 0.22655490040779114, 0.12195570766925812, 0.16498598456382751, 0.18392236530780792, 0.17354930937290192, 0.19174113869667053, 0.19590626657009125, 0.1952698826789856, 0.16737033426761627, 0.12571237981319427, 0.17379088699817657, 0.15908846259117126, 0.2044573873281479, 0.14614848792552948, 0.16350673139095306, 0.1924600899219513, 0.24507863819599152, 0.1515173465013504, 0.2046235054731369, 0.1936655342578888, 0.13635532557964325, 0.210744246840477, 0.1776733547449112, 0.15934409201145172, 0.1763504296541214, 0.24878035485744476, 0.17079395055770874, 0.1960790902376175, 0.16774344444274902, 0.228740394115448, 0.15332089364528656, 0.1918933242559433, 0.16857804358005524, 0.14658936858177185, 0.212324857711792, 0.13488095998764038, 0.12184061110019684, 0.14965775609016418, 0.25336676836013794, 0.21238403022289276, 0.2166547030210495, 0.10941758751869202, 0.24682025611400604, 0.25987666845321655, 0.15198840200901031, 0.20629149675369263, 0.19303067028522491, 0.1701052486896515, 0.18381822109222412, 0.154913529753685, 0.18423108756542206, 0.2302509993314743, 0.16176962852478027, 0.21313226222991943, 0.20357568562030792, 0.22904016077518463, 0.16004447638988495, 0.1765126734972, 0.1484634131193161, 0.14270354807376862, 0.21988490223884583, 0.15700946748256683, 0.20705096423625946, 0.18812167644500732, 0.15144981443881989, 0.09877784550189972, 0.19250307977199554, 0.15727607905864716, 0.22484004497528076, 0.21221232414245605, 0.12261123210191727, 0.1669396162033081, 0.1781051754951477, 0.16061227023601532, 0.16675430536270142, 0.1712411642074585, 0.20090444386005402, 0.20530211925506592, 0.18542464077472687, 0.14433616399765015, 0.21527110040187836, 0.2282419204711914, 0.18931396305561066, 0.18570736050605774, 0.21539142727851868, 0.16413593292236328, 0.25222688913345337, 0.18578849732875824, 0.17018458247184753, 0.18895471096038818, 0.25029170513153076, 0.2272496521472931, 0.1599813550710678, 0.2239464521408081, 0.10550796985626221, 0.14255757629871368, 0.20217163860797882, 0.1165008693933487, 0.13696697354316711, 0.14053957164287567, 0.12745803594589233, 0.16538847982883453, 0.16560231149196625, 0.14045824110507965, 0.15418434143066406, 0.2061389684677124, 0.20050467550754547, 0.12833453714847565, 0.21424396336078644, 0.20304261147975922, 0.21233730018138885, 0.1472155600786209, 0.20337897539138794, 0.16752444207668304, 0.18561625480651855, 0.18686209619045258, 0.21394363045692444, 0.1972619593143463, 0.2106962949037552, 0.1859993189573288, 0.18258482217788696, 0.16994114220142365, 0.16048671305179596, 0.23348639905452728, 0.21977493166923523, 0.20782287418842316, 0.23403310775756836, 0.1692482978105545, 0.23840411007404327, 0.2212926745414734, 0.15481022000312805, 0.13803595304489136, 0.20007658004760742, 0.2229500114917755, 0.16353732347488403, 0.21566374599933624, 0.1866307258605957, 0.1087300106883049, 0.16043193638324738, 0.1852569282054901, 0.10868042707443237, 0.20522384345531464, 0.1351739466190338, 0.15810132026672363, 0.1732703000307083, 0.20381267368793488, 0.1694248616695404, 0.1862316131591797, 0.18841762840747833, 0.14671148359775543, 0.192839577794075, 0.26080024242401123, 0.24698539078235626, 0.22556301951408386, 0.22962181270122528, 0.25149500370025635, 0.1463875025510788, 0.162404403090477, 0.1836879998445511, 0.18334487080574036, 0.2294953167438507, 0.17376554012298584, 0.18470172584056854, 0.18899257481098175, 0.23159430921077728, 0.16385774314403534, 0.13977542519569397, 1.3683016300201416, 2.1079368591308594, 1.4597235918045044, 1.226684808731079, 1.5637699365615845, 2.090954303741455, 1.3798601627349854, 1.5351778268814087, 1.1191694736480713, 1.768790602684021, 1.6744190454483032, 2.3910036087036133, 1.2322595119476318, 2.9353320598602295, 2.1111435890197754, 1.449776291847229, 0.8932459950447083, 1.7423913478851318, 1.4404640197753906, 2.684985876083374, 1.5883610248565674, 2.399264097213745, 1.7915836572647095, 1.1365001201629639, 1.2879345417022705, 1.9513124227523804, 1.5537528991699219, 2.9562840461730957, 1.0715194940567017, 1.6401029825210571, 2.01865553855896, 1.7377967834472656, 1.4277300834655762, 1.6575669050216675, 1.5536596775054932, 1.0495045185089111, 1.8761276006698608, 1.9173216819763184, 0.9335764050483704, 1.6067272424697876, 1.054906964302063, 2.1100268363952637, 1.3539358377456665, 2.6077258586883545, 1.4179818630218506, 1.7966341972351074, 1.5086103677749634, 2.151097059249878, 1.280517816543579, 1.1583712100982666, 1.1209070682525635, 1.2110106945037842, 1.7320690155029297, 1.7189196348190308, 1.0951316356658936, 1.4567838907241821, 1.2597925662994385, 2.1619629859924316, 1.9360473155975342, 1.5564641952514648, 1.1114224195480347, 2.024937868118286, 1.8999810218811035, 1.6444272994995117, 2.0941050052642822, 2.386619806289673, 2.047100305557251, 1.7035295963287354, 0.9632928967475891, 1.937730073928833, 1.336747407913208, 1.8755334615707397, 2.1003711223602295, 1.5705060958862305, 1.7529821395874023, 0.8047406077384949, 1.3925361633300781, 1.4230327606201172, 1.0148437023162842, 1.403070330619812, 1.4759806394577026, 0.8956707715988159, 1.7335054874420166, 1.0083345174789429, 1.2368566989898682, 1.5049612522125244, 1.5523900985717773, 1.358461618423462, 0.9973264932632446, 1.5562264919281006, 1.6196188926696777, 2.006087303161621, 1.560075044631958, 1.2952560186386108, 2.0743603706359863, 0.7744030356407166, 1.231764554977417, 1.8428503274917603, 1.8395622968673706, 1.0803861618041992, 1.5360199213027954, 1.9108918905258179, 1.7294411659240723, 1.0247477293014526, 1.6990978717803955, 1.7934074401855469, 1.1826210021972656, 1.7720131874084473, 1.1152337789535522, 1.9650013446807861, 1.4512706995010376, 1.6608622074127197, 1.5104364156723022, 1.2081894874572754, 1.401652216911316, 1.3773603439331055, 1.4974133968353271, 1.1286362409591675, 2.0329573154449463, 1.3241044282913208, 2.0276663303375244, 1.9866409301757812, 1.7978864908218384, 1.338041067123413, 1.686190128326416, 1.9186910390853882, 2.6184465885162354, 1.2441452741622925, 1.8911787271499634, 1.6540462970733643, 0.9444109201431274, 1.7718900442123413, 1.2266464233398438, 1.7965185642242432, 1.9184856414794922, 1.1379145383834839, 2.0916271209716797, 0.8256559371948242, 1.1076395511627197, 1.5653555393218994, 2.1334972381591797, 1.3950303792953491, 1.563423752784729, 1.3823881149291992, 2.1724908351898193, 1.1091891527175903, 2.049637794494629, 1.8709661960601807, 1.9079254865646362, 1.1910548210144043, 2.0240466594696045, 1.0017095804214478, 1.2377861738204956, 0.8173872232437134, 1.7969938516616821, 1.2015202045440674, 1.3064059019088745, 2.1452715396881104, 0.995253324508667, 1.0910253524780273, 2.1965560913085938, 1.3721163272857666, 1.0725401639938354, 1.9719557762145996, 1.849758505821228, 1.748472809791565, 1.272871732711792, 1.543634295463562, 1.5267584323883057, 1.1564682722091675, 1.6900593042373657, 2.2766504287719727, 2.0300514698028564, 1.5669584274291992, 1.1075164079666138, 0.9429801106452942, 1.298330307006836, 1.8711837530136108, 1.6638884544372559, 1.1737340688705444, 1.8232357501983643, 2.3075037002563477, 1.2904446125030518, 1.5345417261123657, 1.9985042810440063, 1.6281521320343018, 2.1536765098571777, 1.7284759283065796, 1.9918893575668335, 2.4897422790527344, 1.478391408920288, 1.2085456848144531, 1.194558024406433, 1.0231839418411255, 1.2065045833587646, 1.6047706604003906, 1.604602336883545, 1.7402050495147705, 1.3442739248275757, 1.3110893964767456, 1.5169743299484253, 1.4104101657867432, 1.2702792882919312, 1.7513790130615234, 2.9999871253967285, 1.1160662174224854, 1.1129865646362305, 1.3431488275527954, 1.2326624393463135, 1.3298156261444092, 2.3664000034332275, 1.6118202209472656, 1.6882696151733398, 1.9077295064926147, 1.1596739292144775, 1.4604034423828125, 1.7928460836410522, 1.804368257522583, 1.496331810951233, 0.9119561314582825, 1.9032334089279175, 1.5582942962646484, 1.676149845123291, 2.6346166133880615, 1.2903565168380737, 2.489098072052002, 1.335988998413086, 1.3655154705047607, 1.2083042860031128, 1.2031681537628174, 1.3504403829574585, 2.402700185775757, 1.448545217514038, 1.5257641077041626, 1.4334983825683594, 1.3457444906234741, 0.9677203297615051, 2.077130079269409, 1.2176450490951538, 1.7408510446548462, 1.9149515628814697, 1.2139019966125488, 2.0028951168060303, 2.356764793395996, 1.3891069889068604, 1.416382074356079, 2.0528361797332764, 1.84552001953125, 1.992210030555725, 1.8880109786987305, 1.6938427686691284, 1.5302997827529907, 1.8281704187393188, 1.735271692276001, 0.9443351626396179, 1.8420518636703491, 0.7936113476753235, 2.2804975509643555, 1.9731782674789429, 1.082148551940918, 1.8334652185440063, 2.1135895252227783, 1.3364263772964478, 0.8617192506790161, 1.7543920278549194, 1.1055067777633667, 1.5253022909164429, 2.47009015083313, 2.106520652770996, 1.4939378499984741, 1.6306976079940796, 1.8390922546386719, 1.7021772861480713, 1.8680357933044434, 1.7578682899475098, 1.8385059833526611, 1.903082251548767, 1.4906295537948608, 1.6642986536026, 2.1199774742126465, 2.50583815574646, 1.9209705591201782, 1.1834776401519775, 2.1040260791778564, 2.2090413570404053, 2.15415096282959, 1.5924453735351562, 1.8520885705947876, 2.9659042358398438, 1.659829020500183, 2.679474353790283, 1.4325506687164307, 1.4578672647476196, 1.6885924339294434, 1.2463393211364746, 2.870469331741333, 1.5467830896377563, 1.4046545028686523, 1.4136215448379517, 1.4667469263076782, 83.43798828125, 244.0720977783203, 67.72250366210938, 149.2166748046875, 83.84194946289062, 82.71893310546875, 21.84686279296875, 108.08804321289062, 39.369232177734375, 25.83758544921875, 58.86295700073242, 27.13232421875, 94.22669982910156, 180.95079040527344, 159.21942138671875, 238.70274353027344, 54.161678314208984, 59.5161018371582, 214.6840362548828, 109.17996978759766, 303.17828369140625, 44.82752990722656, 115.99331665039062, 368.65069580078125, 120.12700653076172, 260.03082275390625, 404.388427734375, 167.54827880859375, 121.72794342041016, 81.88218688964844, 43.76850509643555, 45.139007568359375, 54.38258743286133, 190.5330047607422, 131.59283447265625, 50.34954833984375, 192.32481384277344, 166.04534912109375, 107.05594635009766, 111.50321197509766, 151.4117889404297, 50.7183837890625, 36.47645568847656, 75.95260620117188, 373.6473388671875, 261.10809326171875, 218.32421875, 51.289608001708984, 39.71075439453125, 89.4828872680664, 31.19915771484375, 111.75029754638672, 142.63912963867188, 107.52989959716797, 47.91961669921875, 145.82550048828125, 142.29721069335938, 139.80235290527344, 169.2145233154297, 52.03247833251953, 104.34780883789062, 31.00091552734375, 353.24578857421875, 151.84669494628906, 117.40657806396484, 36.50251770019531, 27.23394775390625, 29.678651809692383, 28.93400001525879, 91.23702239990234, 216.11886596679688, 137.47618103027344, 43.12689208984375, 153.90313720703125, 154.96878051757812, 70.9476318359375, 142.27728271484375, 159.27503967285156, 42.429447174072266, 154.71029663085938, 68.157958984375, 53.05251693725586, 83.98662567138672, 161.80430603027344, 206.7202911376953, 101.37378692626953, 30.858226776123047, 55.24143600463867, 121.42632293701172, 42.96804428100586, 182.7113037109375, 135.46253967285156, 68.517333984375, 78.715087890625, 168.880615234375, 32.40966796875, 275.1610107421875, 35.9156494140625, 215.22628784179688, 33.00374984741211, 162.01373291015625, 116.9476318359375, 48.36412811279297, 166.64599609375, 50.76947021484375, 119.47541046142578, 113.38263702392578, 76.99066925048828, 71.31230926513672, 135.44744873046875, 57.7578010559082, 56.87807846069336, 169.4066925048828, 115.30575561523438, 191.9854278564453, 159.442626953125, 109.23431396484375, 72.06278991699219, 39.91636657714844, 50.664306640625, 86.69738006591797, 163.37977600097656, 46.52070236206055, 311.48968505859375, 306.8731689453125, 40.29688262939453, 26.375429153442383, 165.85382080078125, 233.8021240234375, 95.63956451416016, 98.78934478759766, 58.00341796875, 44.44707489013672, 156.15924072265625, 72.0716552734375, 56.88427734375, 108.0080337524414, 84.60917663574219, 39.7498779296875, 33.76702880859375, 190.71826171875, 148.56309509277344, 97.49443054199219, 532.0468139648438, 80.53163146972656, 72.24380493164062, 66.87372589111328, 249.26573181152344, 219.01104736328125, 204.74575805664062, 121.51178741455078, 151.60116577148438, 56.6514892578125, 80.44343566894531, 80.40587615966797, 43.80828857421875, 61.58343505859375, 34.75494384765625, 193.6896514892578, 66.94327545166016, 90.79894256591797, 36.40791320800781, 347.9964904785156, 144.70550537109375, 26.863876342773438, 103.791015625, 74.50714111328125, 179.973388671875, 70.02679443359375, 194.5503692626953, 154.124267578125, 68.12936401367188, 31.78448486328125, 82.71163940429688, 57.524139404296875, 90.74310302734375, 180.11062622070312, 108.7845458984375, 159.45086669921875, 71.04315185546875, 74.65859985351562, 154.87200927734375, 89.42822265625, 131.59901428222656, 80.758056640625, 122.90032958984375, 279.9057312011719, 138.10752868652344, 60.884735107421875, 228.7057342529297, 39.89881896972656, 102.03509521484375, 62.0377197265625, 108.19168853759766, 66.77529907226562, 151.47048950195312, 180.6814422607422, 198.07139587402344, 78.148193359375, 292.1615295410156, 71.2208251953125, 137.88458251953125, 27.349700927734375, 74.9883041381836, 51.59060287475586, 160.86016845703125, 31.636857986450195, 68.97128295898438, 42.844970703125, 263.9659423828125, 175.9064483642578, 141.98184204101562, 404.821044921875, 163.85269165039062, 168.76669311523438, 114.95304107666016, 98.8202133178711, 36.44559097290039, 173.1148223876953, 137.70175170898438, 123.2218246459961, 251.3716583251953, 101.17964935302734, 95.74554443359375, 134.143798828125, 123.15019989013672, 296.4778137207031, 111.83946990966797, 270.6925048828125, 39.81071853637695, 518.703125, 181.4017333984375, 67.20849609375, 101.35400390625, 116.22538757324219, 127.4267578125, 42.02490234375, 28.183805465698242, 303.45098876953125, 35.28363037109375, 127.7734375, 329.9970703125, 41.189090728759766, 140.06375122070312, 95.1947250366211, 172.203857421875, 235.73681640625, 227.13937377929688, 27.491039276123047, 163.22686767578125, 33.74757766723633, 152.0708770751953, 179.2747802734375, 204.4735870361328, 255.20664978027344, 166.39710998535156, 39.416748046875, 140.379638671875, 125.8143310546875, 111.1454849243164, 283.0793151855469, 223.9052276611328, 67.46522521972656, 146.44825744628906, 60.614990234375, 192.9449005126953, 125.02587890625, 46.811824798583984, 88.32470703125, 34.600589752197266, 85.7454833984375, 64.41294860839844, 95.06553649902344, 308.52154541015625, 26.1417236328125, 46.68863296508789, 145.59539794921875, 51.429656982421875, 45.77224349975586, 189.16429138183594, 108.30767059326172, 231.04251098632812, 37.51050567626953, 36.36907958984375, 167.5212860107422, 29.01913833618164, 102.47367095947266, 102.12873840332031, 183.2050323486328, 65.6422119140625, 146.05694580078125, 259.09197998046875, 161.69688415527344, 90.01885223388672, 72.67881774902344, 102.61221313476562, 191.02764892578125, 69.71435546875, 99.46826171875, 116.49161529541016, 2.185786724090576, 3.0118987560272217, 1.8017460107803345, 1.540332555770874, 2.4286623001098633, 2.1184823513031006, 1.8096189498901367, 2.438778877258301, 3.2662346363067627, 2.2964656352996826, 1.8212441205978394, 2.3678321838378906, 3.5143041610717773, 2.0513510704040527, 1.8148850202560425, 2.465094804763794, 2.913721799850464, 3.3673906326293945, 2.5548431873321533, 2.4411492347717285, 1.9238674640655518, 2.1221251487731934, 3.0575993061065674, 1.8569177389144897, 2.485567331314087, 2.3378841876983643, 3.4904661178588867, 2.041046142578125, 3.2541961669921875, 2.3324108123779297, 1.7652138471603394, 3.327263832092285, 2.6424973011016846, 3.678251266479492, 2.6078014373779297, 2.466320037841797, 2.820812940597534, 2.8684608936309814, 3.994724988937378, 2.702336311340332, 2.568218946456909, 1.3753210306167603, 2.4651756286621094, 1.9617834091186523, 2.875126838684082, 3.0657970905303955, 2.6921637058258057, 2.9417803287506104, 2.5836381912231445, 2.7140021324157715, 1.8069738149642944, 2.2835569381713867, 2.6846489906311035, 2.0304670333862305, 3.1079626083374023, 2.199598550796509, 2.4328434467315674, 2.1121950149536133, 3.494330644607544, 3.566338062286377, 3.379288911819458, 2.0778913497924805, 2.6376006603240967, 2.655080556869507, 3.596104860305786, 3.016733407974243, 2.0175180435180664, 2.47658634185791, 3.1655235290527344, 2.0096468925476074, 3.6547346115112305, 2.0514605045318604, 4.098907947540283, 2.9242794513702393, 1.6078450679779053, 3.3856899738311768, 1.7129448652267456, 2.2126457691192627, 2.2966842651367188, 1.425679087638855, 2.7571804523468018, 2.5289528369903564, 1.760119080543518, 3.0669665336608887, 1.9760913848876953, 1.790482997894287, 2.8231735229492188, 2.1990747451782227, 2.735734224319458, 2.588841438293457, 2.627073287963867, 2.2028069496154785, 3.705050468444824, 2.0679144859313965, 2.5055019855499268, 1.8653620481491089, 2.35465145111084, 2.3087713718414307, 2.553980827331543, 1.5418633222579956, 2.888324022293091, 2.850534200668335, 2.4447720050811768, 2.704228162765503, 2.173656463623047, 2.463183641433716, 3.458501100540161, 2.41164493560791, 1.7683864831924438, 2.069810628890991, 2.671069383621216, 2.135629177093506, 2.000565528869629, 1.9378881454467773, 1.4210145473480225, 2.102147102355957, 1.8308342695236206, 3.30234694480896, 2.2986857891082764, 1.9428608417510986, 2.821173667907715, 2.7701199054718018, 2.4532344341278076, 2.8315417766571045, 3.189751625061035, 2.5564072132110596, 3.718165159225464, 2.9228909015655518, 2.874769449234009, 2.265726327896118, 2.7769787311553955, 3.1525163650512695, 2.2601659297943115, 2.660487413406372, 2.42635440826416, 2.1318044662475586, 2.4776692390441895, 1.8519524335861206, 1.553198218345642, 2.904200792312622, 3.3972008228302, 1.6234421730041504, 2.70450496673584, 3.1265220642089844, 2.5543789863586426, 2.510788917541504, 1.9091541767120361, 2.174738883972168, 3.1189231872558594, 2.3931477069854736, 1.8468905687332153, 3.011969566345215, 3.204038619995117, 3.147481918334961, 1.9661186933517456, 3.4106059074401855, 3.7597572803497314, 2.44193172454834, 3.1326892375946045, 1.9723061323165894, 3.4433300495147705, 2.048548698425293, 2.7992846965789795, 1.666898488998413, 2.123427629470825, 3.5626275539398193, 1.1759788990020752, 2.7459824085235596, 2.4032888412475586, 2.1566476821899414, 2.452789068222046, 2.0352444648742676, 2.061586618423462, 2.3144302368164062, 3.5843381881713867, 1.7469053268432617, 2.7619426250457764, 3.3993382453918457, 2.210026741027832, 2.061099052429199, 3.1377785205841064, 2.370382070541382, 2.201050043106079, 2.329709053039551, 1.0701475143432617, 3.1687920093536377, 2.337357759475708, 2.4776015281677246, 2.715491771697998, 3.460681676864624, 2.7062430381774902, 2.5362653732299805, 1.5924450159072876, 3.1100659370422363, 2.300126075744629, 1.608689785003662, 2.129012107849121, 2.9800868034362793, 3.16701340675354, 2.493682622909546, 1.087903618812561, 3.762819766998291, 1.7979189157485962, 3.2106738090515137, 2.220364570617676, 3.5465328693389893, 2.7264766693115234, 2.3386106491088867, 1.7896463871002197, 2.2431650161743164, 3.119582414627075, 2.639857053756714, 2.1437501907348633, 2.857285737991333, 1.8046215772628784, 1.9302681684494019, 1.9296213388442993, 3.213162422180176, 1.4515528678894043, 2.126739501953125, 1.4699627161026, 3.849087953567505, 2.0412325859069824, 3.300605058670044, 3.4768896102905273, 3.046563148498535, 2.11196231842041, 2.294283628463745, 1.752061128616333, 2.337217330932617, 3.439423084259033, 2.785954475402832, 1.2257466316223145, 3.2041609287261963, 3.027787446975708, 1.9628304243087769, 3.1389737129211426, 2.6254897117614746, 2.604691743850708, 3.334512233734131, 2.0002317428588867, 2.732011079788208, 1.9349088668823242, 2.593026638031006, 2.356395959854126, 2.0011961460113525, 1.9780319929122925, 3.097064256668091, 2.9483654499053955, 3.3797247409820557, 1.9424608945846558, 3.0335803031921387, 2.501667022705078, 3.2204155921936035, 2.6672027111053467, 2.8208818435668945, 1.7157737016677856, 2.1070358753204346, 1.5251816511154175, 1.3533333539962769, 1.648337721824646, 2.2290146350860596, 3.1590490341186523, 2.974158525466919, 3.2081539630889893, 2.8729889392852783, 2.5363399982452393, 1.195212960243225, 2.347508430480957, 1.5416369438171387, 2.5748672485351562, 2.5443108081817627, 3.0508460998535156, 4.013518810272217, 2.575632333755493, 2.974534511566162, 1.8907173871994019, 2.3514459133148193, 3.117623805999756, 3.439502477645874, 2.204045295715332, 3.0877296924591064, 2.528712749481201, 3.7243263721466064, 3.0620951652526855, 1.4747637510299683, 1.885150671005249, 3.511328935623169, 2.91658878326416, 2.3371808528900146, 1.4148553609848022, 3.415797233581543, 1.8452520370483398, 2.3920507431030273, 3.254498243331909, 0.9564880132675171, 3.535878896713257, 1.7833595275878906, 3.262608051300049, 2.275151252746582, 0.1694480925798416, 0.16341565549373627, 0.17905379831790924, 0.1765441596508026, 0.23343069851398468, 0.13911288976669312, 0.1706436574459076, 0.23064811527729034, 0.23111401498317719, 0.16567271947860718, 0.24223433434963226, 0.14276887476444244, 0.1853235960006714, 0.17231875658035278, 0.17812280356884003, 0.2294904589653015, 0.21584494411945343, 0.18517017364501953, 0.21545153856277466, 0.2374439537525177, 0.16592927277088165, 0.21049420535564423, 0.16601502895355225, 0.18704429268836975, 0.12652485072612762, 0.2258520871400833, 0.18437345325946808, 0.16116313636302948, 0.1683322936296463, 0.24744921922683716, 0.2057514488697052, 0.24829868972301483, 0.10223591327667236, 0.24481232464313507, 0.14484722912311554, 0.12261167168617249, 0.16375644505023956, 0.13214115798473358, 0.09773948788642883, 0.29122328758239746, 0.15484675765037537, 0.1736055314540863, 0.19361558556556702, 0.14531733095645905, 0.162927508354187, 0.15611149370670319, 0.17865917086601257, 0.1414625346660614, 0.15035247802734375, 0.18957877159118652, 0.18036937713623047, 0.146736279129982, 0.19583842158317566, 0.266886442899704, 0.12798619270324707, 0.1557149440050125, 0.26632171869277954, 0.16195864975452423, 0.24686338007450104, 0.23495347797870636, 0.1513138860464096, 0.19709117710590363, 0.13740824162960052, 0.17470760643482208, 0.24403876066207886, 0.19564250111579895, 0.17683391273021698, 0.21531176567077637, 0.12880229949951172, 0.20773622393608093, 0.22872859239578247, 0.18711379170417786, 0.18766185641288757, 0.27452370524406433, 0.23470640182495117, 0.28970056772232056, 0.19118010997772217, 0.17234691977500916, 0.16305497288703918, 0.17302104830741882, 0.1352950930595398, 0.22425414621829987, 0.19251476228237152, 0.19303083419799805, 0.179554745554924, 0.1707267016172409, 0.2074117660522461, 0.19326110184192657, 0.21367381513118744, 0.16523639857769012, 0.11532306671142578, 0.21902646124362946, 0.1357751041650772, 0.17042595148086548, 0.24206885695457458, 0.20004752278327942, 0.192295104265213, 0.1952654868364334, 0.16592448949813843, 0.17243340611457825, 0.20311900973320007, 0.10555046796798706, 0.11703266948461533, 0.18676269054412842, 0.20298632979393005, 0.21054241061210632, 0.17806941270828247, 0.2069169133901596, 0.14797130227088928, 0.16136570274829865, 0.1983884572982788, 0.2042333483695984, 0.1398594230413437, 0.12418278306722641, 0.17568238079547882, 0.19898737967014313, 0.2137822061777115, 0.1706506311893463, 0.19792911410331726, 0.2292156219482422, 0.20310333371162415, 0.13967472314834595, 0.13819585740566254, 0.17330455780029297, 0.1359948217868805, 0.15803568065166473, 0.17986081540584564, 0.1874343305826187, 0.16695883870124817, 0.16426189243793488, 0.21296073496341705, 0.1685086041688919, 0.23916572332382202, 0.16434118151664734, 0.19283874332904816, 0.1664104014635086, 0.18797416985034943, 0.16877074539661407, 0.21595275402069092, 0.20899780094623566, 0.16374903917312622, 0.17661850154399872, 0.20597952604293823, 0.15094009041786194, 0.17559970915317535, 0.23273921012878418, 0.16062726080417633, 0.18149875104427338, 0.2386045902967453, 0.24174539744853973, 0.16743560135364532, 0.15051095187664032, 0.22696304321289062, 0.2345944494009018, 0.16433098912239075, 0.21239420771598816, 0.11656308174133301, 0.2204790860414505, 0.2444663792848587, 0.14331158995628357, 0.18123894929885864, 0.1711154580116272, 0.20703938603401184, 0.146684467792511, 0.18586039543151855, 0.20759665966033936, 0.24577277898788452, 0.22064344584941864, 0.16437339782714844, 0.17618337273597717, 0.23193156719207764, 0.2449682503938675, 0.19957324862480164, 0.1724262237548828, 0.195292666554451, 0.24409030377864838, 0.17733561992645264, 0.20921847224235535, 0.21785643696784973, 0.20850928127765656, 0.28921574354171753, 0.1280108094215393, 0.1488332599401474, 0.12126130610704422, 0.1542355716228485, 0.18066494166851044, 0.20639848709106445, 0.1557585746049881, 0.11886458098888397, 0.17746001482009888, 0.21707002818584442, 0.15402865409851074, 0.1637800931930542, 0.21245424449443817, 0.22411376237869263, 0.18770083785057068, 0.18879079818725586, 0.16685782372951508, 0.17359672486782074, 0.24733617901802063, 0.1823432892560959, 0.22787688672542572, 0.20039458572864532, 0.2231801152229309, 0.2259073257446289, 0.20265740156173706, 0.2353866845369339, 0.18062281608581543, 0.1034979298710823, 0.21023723483085632, 0.2662203907966614, 0.1200719028711319, 0.19228707253932953, 0.20897167921066284, 0.2147710919380188, 0.1741100698709488, 0.22124893963336945, 0.20287318527698517, 0.24141530692577362, 0.11279094219207764, 0.15664522349834442, 0.22140063345432281, 0.15138621628284454, 0.16706408560276031, 0.174820214509964, 0.14339686930179596, 0.18898630142211914, 0.18801669776439667, 0.2070567011833191, 0.1790296882390976, 0.1453162580728531, 0.16190099716186523, 0.1383161097764969, 0.13705845177173615, 0.14053069055080414, 0.23998339474201202, 0.11837394535541534, 0.2257082164287567, 0.15199899673461914, 0.1963256150484085, 0.22318868339061737, 0.24756473302841187, 0.2554810643196106, 0.20821231603622437, 0.16185262799263, 0.20108455419540405, 0.2023111879825592, 0.2557869255542755, 0.16352863609790802, 0.18040324747562408, 0.2592228949069977, 0.1985928863286972, 0.15446771681308746, 0.2535529136657715, 0.15539993345737457, 0.1643732488155365, 0.1320202648639679, 0.18836675584316254, 0.14450979232788086, 0.2567712962627411, 0.1637025773525238, 0.08067911863327026, 0.17481838166713715, 0.1759513020515442, 0.17066526412963867, 0.16890648007392883, 0.19031287729740143, 0.24096599221229553, 0.13063590228557587, 0.2649132013320923, 0.16912421584129333, 0.18775208294391632, 0.14578859508037567, 0.18338866531848907, 0.25339293479919434, 0.24592240154743195, 0.11194532364606857, 0.20255595445632935, 0.25565603375434875, 0.17010368406772614, 0.20875151455402374, 0.2100561410188675, 0.19848036766052246, 0.21063287556171417, 0.1810174584388733, 0.23305638134479523, 0.18678225576877594, 0.22050915658473969, 0.22399985790252686, 0.21271532773971558, 0.20808856189250946, 0.14863033592700958, 0.16038274765014648, 0.17157573997974396, 0.23317310214042664, 0.18772448599338531, 0.22997523844242096, 0.10098405927419662, 0.1703568547964096, 0.19296972453594208, 1.8987994194030762, 1.0774428844451904, 1.2805824279785156, 1.439752459526062, 1.6349836587905884, 2.0341110229492188, 2.12583327293396, 1.1398301124572754, 1.8026260137557983, 1.9197965860366821, 2.4808502197265625, 1.7122925519943237, 1.597629189491272, 2.2921457290649414, 2.161367416381836, 1.2961441278457642, 1.9970861673355103, 1.2763428688049316, 0.7426974177360535, 1.8074144124984741, 1.2424613237380981, 1.6190290451049805, 1.3001333475112915, 3.6086342334747314, 2.0711991786956787, 1.555696964263916, 1.907501459121704, 1.7285343408584595, 1.6690119504928589, 1.0499719381332397, 1.1535077095031738, 1.0557703971862793, 1.2208685874938965, 1.2886959314346313, 1.877005934715271, 1.7229403257369995, 1.5167171955108643, 1.5458306074142456, 1.9127695560455322, 2.149946451187134, 2.0905075073242188, 1.4445393085479736, 3.0381603240966797, 1.658058762550354, 1.75664222240448, 1.5895299911499023, 1.663627028465271, 1.7031292915344238, 1.3674354553222656, 1.2846065759658813, 1.8897291421890259, 1.8544018268585205, 2.1092069149017334, 1.618428111076355, 1.1632815599441528, 2.1865158081054688, 1.8310329914093018, 1.894311785697937, 2.0338263511657715, 1.143859624862671, 1.5488146543502808, 1.9704102277755737, 1.5748237371444702, 1.4756401777267456, 1.5806543827056885, 1.4713350534439087, 1.0932856798171997, 1.6906157732009888, 2.0066287517547607, 1.2417607307434082, 2.466437339782715, 1.6980681419372559, 1.5939213037490845, 2.8039474487304688, 0.9456555247306824, 1.9663375616073608, 1.3365888595581055, 1.4614826440811157, 1.590692400932312, 1.2674096822738647, 1.2766159772872925, 1.7821012735366821, 1.1603343486785889, 1.2374199628829956, 1.5862655639648438, 2.309227705001831, 0.9513190388679504, 1.9803460836410522, 2.6919543743133545, 1.2249001264572144, 2.287226438522339, 2.761802911758423, 1.4820095300674438, 1.281891107559204, 1.0419445037841797, 1.5145310163497925, 1.3293946981430054, 1.9591172933578491, 1.082595944404602, 1.8188875913619995, 2.1188642978668213, 1.182734489440918, 1.8634836673736572, 2.49871826171875, 1.7859679460525513, 1.2061219215393066, 1.5214729309082031, 1.203460931777954, 1.2843067646026611, 1.182547926902771, 1.1223187446594238, 1.6330375671386719, 1.784641981124878, 1.9857441186904907, 2.219144105911255, 1.7423981428146362, 1.726837158203125, 2.2425622940063477, 1.5857378244400024, 1.2522151470184326, 2.1564817428588867, 1.9850783348083496, 1.6299244165420532, 2.0283079147338867, 1.57421875, 1.745918869972229, 1.9917980432510376, 1.2352573871612549, 2.373504638671875, 1.3344001770019531, 1.047492504119873, 1.7727084159851074, 1.584775686264038, 1.7298333644866943, 2.927507162094116, 0.9794467091560364, 1.2108603715896606, 2.21488356590271, 1.3859115839004517, 1.4304256439208984, 1.4306821823120117, 1.4264084100723267, 2.0093395709991455, 1.748507022857666, 1.4976927042007446, 2.055422306060791, 2.3930723667144775, 1.8736904859542847, 2.3912341594696045, 1.2568655014038086, 1.1946648359298706, 1.3536694049835205, 1.6160706281661987, 1.9780819416046143, 2.3051915168762207, 1.9135977029800415, 1.9354796409606934, 1.7792659997940063, 1.071433424949646, 1.0794248580932617, 2.0886731147766113, 1.9705418348312378, 1.1794993877410889, 2.122718572616577, 1.4537911415100098, 1.7482807636260986, 1.380414366722107, 1.3836435079574585, 1.2506378889083862, 1.1997498273849487, 1.8120167255401611, 1.9734939336776733, 2.2679085731506348, 1.4450639486312866, 1.3223912715911865, 1.8686290979385376, 1.3203036785125732, 1.7542955875396729, 2.1156005859375, 1.6917181015014648, 1.5804646015167236, 1.0790469646453857, 1.7807247638702393, 1.7852239608764648, 2.5659501552581787, 1.4743067026138306, 1.926015853881836, 1.6421990394592285, 1.4578453302383423, 2.274737596511841, 1.1959235668182373, 0.9302150011062622, 1.2924368381500244, 0.9224404692649841, 1.8992578983306885, 2.270071268081665, 1.3907015323638916, 1.7793545722961426, 1.390907883644104, 1.8670034408569336, 1.4196439981460571, 1.8090559244155884, 1.1865795850753784, 1.3237285614013672, 1.8426941633224487, 1.951782464981079, 2.1929144859313965, 1.7900670766830444, 1.2896875143051147, 2.2715682983398438, 1.6324741840362549, 1.4512087106704712, 1.5094757080078125, 1.5350509881973267, 1.642595648765564, 1.8769975900650024, 1.7409155368804932, 1.6459604501724243, 0.8556649088859558, 1.5077651739120483, 2.4246814250946045, 1.196545958518982, 1.7900216579437256, 1.2444744110107422, 1.3558305501937866, 0.9947469830513, 1.9550951719284058, 1.9495294094085693, 1.5349810123443604, 1.4018703699111938, 1.5228039026260376, 2.0161092281341553, 1.7526620626449585, 1.9731194972991943, 1.4649658203125, 1.3691130876541138, 1.0323442220687866, 1.3861281871795654, 2.3416638374328613, 1.3392448425292969, 1.706812858581543, 0.9892001152038574, 1.6945310831069946, 1.1727784872055054, 1.7735347747802734, 1.5002901554107666, 1.885626196861267, 1.399863839149475, 1.7452760934829712, 1.1124128103256226, 2.1553778648376465, 1.8467925786972046, 2.4162380695343018, 1.8234513998031616, 1.2632055282592773, 1.0268875360488892, 1.5921179056167603, 1.3325103521347046, 1.5725202560424805, 1.3752564191818237, 1.6674752235412598, 1.7915053367614746, 1.5861669778823853, 1.324676752090454, 2.05949068069458, 2.0329489707946777, 1.5683122873306274, 1.6919704675674438, 2.4964005947113037, 2.0288379192352295, 1.1296075582504272, 1.6454582214355469, 1.6073297262191772, 1.027477502822876, 1.180869460105896, 1.022072434425354, 1.4394080638885498, 1.319879174232483, 1.3936620950698853, 1.8066400289535522, 1.4575709104537964, 2.8931901454925537, 1.3146828413009644, 2.252117395401001, 1.4572603702545166, 1.1451858282089233, 1.4203842878341675, 2.104844808578491, 1.4429495334625244, 1.393174409866333, 1.842388391494751, 1.8541662693023682, 1.899334192276001, 1.2673906087875366, 2.111328125, 1.8250479698181152, 1.6923786401748657, 1.4311573505401611, 2.3178963661193848, 1.7662590742111206, 57.35247802734375, 49.351863861083984, 61.603172302246094, 44.904109954833984, 78.08776092529297, 74.01927947998047, 74.44546508789062, 34.90443420410156, 285.7540283203125, 126.33538818359375, 40.048919677734375, 76.39308166503906, 137.9710693359375, 32.871337890625, 60.96893310546875, 40.32281494140625, 117.33577728271484, 94.84173583984375, 106.21045684814453, 254.0249786376953, 127.2796630859375, 73.60502624511719, 125.07575225830078, 181.01361083984375, 135.06578063964844, 119.41561889648438, 148.09368896484375, 193.02456665039062, 134.06553649902344, 235.17442321777344, 95.84708404541016, 309.28277587890625, 94.3402099609375, 59.119476318359375, 30.785531997680664, 138.84765625, 299.7181091308594, 173.61587524414062, 154.28750610351562, 110.62686920166016, 58.34528350830078, 110.91482543945312, 220.4684295654297, 323.88671875, 75.76048278808594, 125.97492218017578, 42.55867004394531, 200.5751190185547, 221.61248779296875, 100.2513656616211, 117.23365783691406, 37.23089599609375, 126.91305541992188, 179.7715606689453, 55.913143157958984, 247.8285675048828, 45.88226318359375, 256.40936279296875, 66.018798828125, 83.43677520751953, 125.65775299072266, 161.9001007080078, 74.89111328125, 121.86634826660156, 179.1656951904297, 31.16680908203125, 76.52840423583984, 259.763916015625, 174.9310302734375, 67.89710998535156, 161.80975341796875, 86.390869140625, 86.7895278930664, 86.92205810546875, 69.6815185546875, 28.504642486572266, 171.1674041748047, 149.8406982421875, 169.08253479003906, 313.7746887207031, 40.37561798095703, 185.59716796875, 99.27557373046875, 96.67788696289062, 123.43084716796875, 214.4850311279297, 275.2686767578125, 279.9913330078125, 125.82622528076172, 165.6026153564453, 72.5073013305664, 173.72152709960938, 76.80905151367188, 183.88340759277344, 53.619789123535156, 93.08110809326172, 169.28721618652344, 26.42572021484375, 62.52435302734375, 141.69610595703125, 77.61033630371094, 133.5340576171875, 110.86962890625, 299.6780700683594, 144.8369140625, 185.8163604736328, 64.5958251953125, 125.4111328125, 126.1181640625, 45.64046859741211, 81.3741226196289, 29.7503662109375, 113.0013427734375, 234.6739044189453, 144.84600830078125, 83.037841796875, 74.10693359375, 111.0297622680664, 30.010223388671875, 288.2860107421875, 145.04443359375, 110.2166748046875, 259.81011962890625, 170.1251983642578, 58.71670150756836, 66.38562774658203, 76.30902099609375, 33.57571029663086, 275.13037109375, 162.54623413085938, 46.21567916870117, 101.62163543701172, 89.15503692626953, 106.58796691894531, 45.56307601928711, 45.204647064208984, 115.09111785888672, 133.14422607421875, 92.08556365966797, 136.001953125, 59.07615280151367, 311.8643798828125, 64.14141082763672, 107.5296630859375, 220.7205352783203, 106.04470825195312, 103.0628890991211, 216.75732421875, 198.1265411376953, 31.268556594848633, 24.43741226196289, 96.60858154296875, 181.2572021484375, 261.0186767578125, 58.40686798095703, 95.1462173461914, 478.6039733886719, 74.71923828125, 223.52093505859375, 105.89736938476562, 27.89105224609375, 35.880191802978516, 44.20654296875, 58.05315399169922, 46.8902587890625, 186.564208984375, 111.27714538574219, 57.3551025390625, 149.52679443359375, 104.67023468017578, 89.08525848388672, 323.10162353515625, 237.84539794921875, 92.18374633789062, 142.9189453125, 204.4073028564453, 130.6455078125, 61.99909973144531, 346.9913635253906, 48.47971725463867, 107.11021423339844, 201.92529296875, 149.75352478027344, 141.40966796875, 101.96987915039062, 27.568050384521484, 136.4490966796875, 194.0811309814453, 79.82540130615234, 131.53985595703125, 139.21697998046875, 47.391902923583984, 104.41921997070312, 59.40217208862305, 41.0551643371582, 139.5873565673828, 28.64068603515625, 27.681724548339844, 240.97972106933594, 38.683349609375, 51.50612258911133, 42.60466766357422, 55.45097351074219, 68.86607360839844, 242.67288208007812, 231.62615966796875, 208.7613067626953, 112.49468231201172, 235.68614196777344, 134.07867431640625, 46.003231048583984, 138.36819458007812, 148.31211853027344, 293.3875732421875, 151.4288787841797, 36.22845458984375, 57.08465576171875, 29.49249267578125, 27.983642578125, 182.2707061767578, 170.66143798828125, 59.433837890625, 185.39651489257812, 36.96845245361328, 216.90391540527344, 104.23218536376953, 164.13186645507812, 33.24026107788086, 75.34404754638672, 95.06119537353516, 37.1138916015625, 115.25251770019531, 38.56073760986328, 141.29608154296875, 140.63531494140625, 58.99734115600586, 32.99311065673828, 175.66574096679688, 28.842044830322266, 112.8739013671875, 30.32763671875, 46.455047607421875, 119.23828887939453, 208.32373046875, 110.74058532714844, 196.9757843017578, 152.93569946289062, 112.121337890625, 248.97589111328125, 99.86058044433594, 121.6522216796875, 154.31033325195312, 179.15005493164062, 304.7799987792969, 129.21006774902344, 141.91921997070312, 35.743621826171875, 208.6957550048828, 134.0350341796875, 136.4613037109375, 46.204349517822266, 56.79052734375, 31.9324951171875, 36.37481689453125, 56.55155944824219, 233.93505859375, 88.36827850341797, 36.80952072143555, 99.92523193359375, 142.32138061523438, 215.9324951171875, 69.12206268310547, 42.59366226196289, 111.10850524902344, 22.17254638671875, 128.27117919921875, 125.33438873291016, 58.36912155151367, 101.151611328125, 30.948148727416992, 89.49590301513672, 164.69464111328125, 30.538375854492188, 283.14300537109375, 80.3956298828125, 32.64188003540039, 47.60396957397461, 32.9129638671875, 130.0365753173828, 26.55023956298828, 97.33634185791016, 52.92593002319336, 54.79071044921875, 32.92646026611328, 41.063602447509766, 116.25150299072266, 79.89701843261719, 227.90167236328125, 72.15594482421875, 207.4181365966797, 1.9517143964767456, 3.3102505207061768, 1.301705241203308, 1.8408328294754028, 2.5331051349639893, 2.6647746562957764, 1.5475174188613892, 2.632798433303833, 1.4681310653686523, 2.2240636348724365, 3.3799543380737305, 1.82262122631073, 3.2629406452178955, 1.438017725944519, 3.2813057899475098, 1.384965181350708, 2.799426317214966, 2.8056492805480957, 1.9983035326004028, 2.3193771839141846, 2.917645215988159, 2.6409826278686523, 2.8702898025512695, 2.8089306354522705, 2.4738502502441406, 1.8790639638900757, 2.7244348526000977, 1.838797926902771, 1.5695455074310303, 2.0922012329101562, 3.729302167892456, 1.2790638208389282, 1.9915401935577393, 2.573796033859253, 1.8078815937042236, 2.8876049518585205, 2.0472095012664795, 2.8984155654907227, 1.6358698606491089, 2.1354634761810303, 2.164172410964966, 2.206157684326172, 3.756809949874878, 2.5898492336273193, 2.683516263961792, 2.137274742126465, 1.848430871963501, 2.631395101547241, 3.5916643142700195, 2.1354422569274902, 2.8787949085235596, 2.532325029373169, 2.928881883621216, 1.9947309494018555, 3.3897228240966797, 2.5996813774108887, 2.5227890014648438, 2.0343263149261475, 2.1472997665405273, 4.075291633605957, 3.5553808212280273, 3.0360937118530273, 3.795974016189575, 3.197213649749756, 3.5392065048217773, 2.980787992477417, 2.1911568641662598, 2.3930230140686035, 2.1097476482391357, 1.5564031600952148, 2.59291934967041, 3.309257984161377, 2.200718879699707, 2.0876901149749756, 1.6475276947021484, 2.114199638366699, 2.180259943008423, 1.7348647117614746, 1.6336345672607422, 3.3441531658172607, 1.6673601865768433, 1.9181785583496094, 2.600335121154785, 2.794419765472412, 2.6400134563446045, 2.21290922164917, 2.930934429168701, 2.8519012928009033, 2.1291000843048096, 2.7550299167633057, 2.6911346912384033, 2.7268948554992676, 2.4543559551239014, 2.3815011978149414, 2.610272169113159, 3.0627472400665283, 2.356137275695801, 2.7771332263946533, 1.7152682542800903, 1.6436704397201538, 2.753657579421997, 2.6627352237701416, 2.4810214042663574, 3.0891201496124268, 2.482668876647949, 1.6272430419921875, 2.433812141418457, 2.945202589035034, 1.7928811311721802, 1.319601058959961, 2.1734001636505127, 1.8640127182006836, 3.432767152786255, 2.0349950790405273, 3.917487144470215, 1.7543076276779175, 2.271136999130249, 3.133392572402954, 3.3237478733062744, 1.8417463302612305, 3.191166400909424, 2.498561382293701, 2.1186304092407227, 2.2409982681274414, 2.9079952239990234, 2.574690580368042, 2.654179573059082, 3.4040403366088867, 1.9266327619552612, 2.2029218673706055, 2.8018176555633545, 2.887040376663208, 1.8528738021850586, 1.7862180471420288, 2.3530964851379395, 3.0371923446655273, 2.41414737701416, 2.1809873580932617, 2.872882604598999, 2.69956111907959, 1.8570950031280518, 2.0013303756713867, 2.710217237472534, 2.255873680114746, 2.0776937007904053, 3.0336124897003174, 2.342108726501465, 2.6414408683776855, 3.2546911239624023, 1.3657140731811523, 3.34560489654541, 1.7454471588134766, 2.8998939990997314, 2.404057502746582, 3.166638135910034, 2.3753533363342285, 1.7647056579589844, 2.7630059719085693, 3.2901904582977295, 2.8459911346435547, 2.0499658584594727, 1.613139271736145, 2.641404628753662, 1.912710428237915, 1.9872559309005737, 1.3303519487380981, 3.413740873336792, 1.9121750593185425, 2.298720598220825, 2.2893667221069336, 1.9616925716400146, 2.535764217376709, 2.018315315246582, 3.6678788661956787, 2.7187492847442627, 2.6475377082824707, 2.7147624492645264, 2.2630841732025146, 1.2096929550170898, 2.820188283920288, 2.910754442214966, 2.981786012649536, 1.7022231817245483, 1.9301186800003052, 1.6851471662521362, 1.04149329662323, 2.990123748779297, 2.6335039138793945, 2.4480209350585938, 2.2865285873413086, 1.521553874015808, 3.7319140434265137, 2.976518392562866, 2.362377643585205, 1.583878755569458, 2.5093905925750732, 3.168231248855591, 1.9007402658462524, 3.289212465286255, 1.801344871520996, 2.9885592460632324, 3.6865336894989014, 1.3789631128311157, 1.8260749578475952, 1.7683323621749878, 2.974900722503662, 3.1884286403656006, 1.9074316024780273, 2.793309211730957, 3.3093414306640625, 2.9208672046661377, 2.413959264755249, 1.8362702131271362, 3.262962579727173, 3.7033791542053223, 1.9468145370483398, 3.0747838020324707, 2.89945125579834, 2.32879638671875, 2.03610897064209, 2.153611421585083, 2.1747500896453857, 2.5768115520477295, 2.39681339263916, 3.7671940326690674, 3.2455785274505615, 1.5805169343948364, 2.1834089756011963, 1.3380755186080933, 2.130289077758789, 2.153378486633301, 2.555882453918457, 3.392054557800293, 2.4069671630859375, 1.8929381370544434, 3.5182316303253174, 1.6232959032058716, 2.1425962448120117, 2.5253708362579346, 2.702019691467285, 2.0612897872924805, 2.2452216148376465, 2.3322389125823975, 3.072384834289551, 3.418572425842285, 2.9353179931640625, 2.6718785762786865, 1.5949722528457642, 3.983614921569824, 3.1989283561706543, 2.420098304748535, 2.615999698638916, 2.5991814136505127, 2.8558642864227295, 1.9984166622161865, 1.910683512687683, 1.8770910501480103, 1.9885156154632568, 2.062464714050293, 1.9678210020065308, 2.4702000617980957, 1.9958643913269043, 2.264817237854004, 3.471505641937256, 3.6126813888549805, 2.5022690296173096, 1.5144140720367432, 2.050780773162842, 3.263463020324707, 2.665531635284424, 2.7146294116973877, 1.6260185241699219, 1.7395761013031006, 2.677374839782715, 1.9518423080444336, 1.8343993425369263, 2.8807404041290283, 2.09909987449646, 2.122187852859497, 1.8610674142837524, 1.668074607849121, 1.4427424669265747, 2.393817186355591, 2.890623092651367, 2.020358085632324, 3.028704881668091, 3.853369951248169, 2.6239640712738037, 3.0086565017700195, 3.4456121921539307, 2.457839250564575, 3.058893918991089, 2.6364192962646484, 2.291327476501465, 2.5401623249053955, 1.5818750858306885, 2.03981876373291, 3.481318235397339, 2.6171412467956543, 1.8012017011642456, 0.1728191375732422, 0.17165906727313995, 0.24835491180419922, 0.17110010981559753, 0.19674746692180634, 0.13864101469516754, 0.21792998909950256, 0.18062420189380646, 0.17662692070007324, 0.14605647325515747, 0.14307443797588348, 0.15691031515598297, 0.19112423062324524, 0.24797163903713226, 0.23654299974441528, 0.21806392073631287, 0.2474345713853836, 0.24684982001781464, 0.19705939292907715, 0.1797870397567749, 0.12724430859088898, 0.16170966625213623, 0.21638129651546478, 0.1714608371257782, 0.1530882716178894, 0.18730156123638153, 0.1262635588645935, 0.19433997571468353, 0.18374334275722504, 0.2269975244998932, 0.11547569930553436, 0.2121705561876297, 0.13502229750156403, 0.22367049753665924, 0.13684308528900146, 0.20987975597381592, 0.15991412103176117, 0.15682066977024078, 0.2044689953327179, 0.12793980538845062, 0.17999251186847687, 0.13517993688583374, 0.21809254586696625, 0.15504206717014313, 0.16864241659641266, 0.20633476972579956, 0.12300801277160645, 0.21085263788700104, 0.14896291494369507, 0.18757112324237823, 0.1624564826488495, 0.1404094696044922, 0.17160648107528687, 0.19874626398086548, 0.2084544152021408, 0.15365076065063477, 0.1829080581665039, 0.22960680723190308, 0.12693312764167786, 0.13300973176956177, 0.1646413803100586, 0.1147552877664566, 0.23905380070209503, 0.1993798017501831, 0.2435523122549057, 0.21810860931873322, 0.13113997876644135, 0.19328758120536804, 0.1977870762348175, 0.16960017383098602, 0.16187970340251923, 0.2476208508014679, 0.17574992775917053, 0.15800030529499054, 0.21519240736961365, 0.11562011390924454, 0.23865455389022827, 0.1601940542459488, 0.11868499219417572, 0.22147269546985626, 0.25819170475006104, 0.1979280263185501, 0.18860432505607605, 0.1789223700761795, 0.24927332997322083, 0.1987878382205963, 0.16676650941371918, 0.192585751414299, 0.15283386409282684, 0.11767319589853287, 0.2032867819070816, 0.23965604603290558, 0.19473977386951447, 0.1662941724061966, 0.1871461421251297, 0.14100861549377441, 0.17960231006145477, 0.12164306640625, 0.17763593792915344, 0.16386374831199646, 0.18283653259277344, 0.17703182995319366, 0.20538073778152466, 0.2011244297027588, 0.2423734962940216, 0.14558124542236328, 0.15593929588794708, 0.1981268972158432, 0.20323532819747925, 0.1406986117362976, 0.24076689779758453, 0.1662614345550537, 0.2064165472984314, 0.149607315659523, 0.16928015649318695, 0.19438917934894562, 0.171004980802536, 0.2805233299732208, 0.15903036296367645, 0.22199685871601105, 0.19851432740688324, 0.24397465586662292, 0.19563929736614227, 0.2583807706832886, 0.22993633151054382, 0.1554790884256363, 0.18974994122982025, 0.19515156745910645, 0.21654771268367767, 0.2634908854961395, 0.2071089744567871, 0.23712222278118134, 0.22849655151367188, 0.16987738013267517, 0.1439237892627716, 0.15637199580669403, 0.13259045779705048, 0.14624591171741486, 0.17527063190937042, 0.1895839273929596, 0.17772217094898224, 0.2052653282880783, 0.1219567283987999, 0.1827210634946823, 0.17450293898582458, 0.18706955015659332, 0.16110286116600037, 0.14065761864185333, 0.19968554377555847, 0.19238880276679993, 0.21752870082855225, 0.20100711286067963, 0.24398650228977203, 0.23344926536083221, 0.2592882513999939, 0.13619957864284515, 0.2255609780550003, 0.1936134546995163, 0.1206091120839119, 0.15199685096740723, 0.18454387784004211, 0.19782912731170654, 0.1764795482158661, 0.24766425788402557, 0.17097419500350952, 0.15541252493858337, 0.20914143323898315, 0.1448742002248764, 0.20038849115371704, 0.17394863069057465, 0.19505953788757324, 0.25737544894218445, 0.13365179300308228, 0.21348121762275696, 0.18601417541503906, 0.2233247309923172, 0.16992183029651642, 0.20313195884227753, 0.1999107152223587, 0.1968134194612503, 0.18213684856891632, 0.21821968257427216, 0.16390056908130646, 0.13794690370559692, 0.2220975011587143, 0.17357237637043, 0.15207965672016144, 0.2172040492296219, 0.1834120750427246, 0.1726342737674713, 0.18203367292881012, 0.1346762478351593, 0.2249108850955963, 0.15862634778022766, 0.21011081337928772, 0.22595632076263428, 0.16553813219070435, 0.16546377539634705, 0.21428735554218292, 0.18858517706394196, 0.27066394686698914, 0.2701697051525116, 0.13336849212646484, 0.1782057136297226, 0.176776722073555, 0.21578069031238556, 0.17474442720413208, 0.17185340821743011, 0.18430045247077942, 0.18693843483924866, 0.11702984571456909, 0.1755543053150177, 0.1814933866262436, 0.2037096917629242, 0.2161652147769928, 0.20713332295417786, 0.18003806471824646, 0.16393955051898956, 0.21290546655654907, 0.1956668198108673, 0.21658551692962646, 0.23824410140514374, 0.24578920006752014, 0.2344788908958435, 0.19647525250911713, 0.1615923047065735, 0.2317604273557663, 0.15844787657260895, 0.16760696470737457, 0.20571982860565186, 0.14884042739868164, 0.28349021077156067, 0.1758958399295807, 0.19366656243801117, 0.2201446145772934, 0.1392655223608017, 0.2136116325855255, 0.24068978428840637, 0.18101456761360168, 0.1438395082950592, 0.2000841498374939, 0.2470213621854782, 0.2498898208141327, 0.18971644341945648, 0.17578767240047455, 0.25053656101226807, 0.1766289621591568, 0.23570500314235687, 0.17894025146961212, 0.14934293925762177, 0.1924295723438263, 0.17626738548278809, 0.18707424402236938, 0.2246919423341751, 0.13717429339885712, 0.18986140191555023, 0.1274901181459427, 0.21501289308071136, 0.1126900240778923, 0.20961962640285492, 0.12941552698612213, 0.20761118829250336, 0.2639434039592743, 0.25105148553848267, 0.13194110989570618, 0.21255888044834137, 0.14158646762371063, 0.18351244926452637, 0.17568667232990265, 0.22528570890426636, 0.0996285229921341, 0.20446345210075378, 0.2240169793367386, 0.15994559228420258, 0.1396942138671875, 0.21596527099609375, 0.2278042584657669, 0.1928335726261139, 0.24473391473293304, 0.25341716408729553, 0.2649649381637573, 0.2171078473329544, 0.20679394900798798, 0.16155456006526947, 0.15775370597839355, 0.2494494616985321, 0.2328340858221054, 0.19835889339447021, 0.1709216982126236, 0.16155879199504852, 0.20171260833740234, 0.162648543715477, 0.17028892040252686, 0.12019747495651245, 0.18234463036060333, 0.13811767101287842, 0.19947469234466553, 0.19521141052246094, 0.24585965275764465, 0.19901220500469208, 1.2697107791900635, 2.1560165882110596, 1.3923128843307495, 2.944485902786255, 1.342565894126892, 1.712664008140564, 1.5004513263702393, 1.5028648376464844, 1.0603535175323486, 1.4147485494613647, 1.9322954416275024, 1.9133559465408325, 2.521028995513916, 2.003242254257202, 1.6133657693862915, 1.9883909225463867, 1.989976167678833, 1.545349359512329, 2.3964314460754395, 1.98509681224823, 1.9958019256591797, 1.83098566532135, 2.193706512451172, 1.283488392829895, 2.5524351596832275, 1.288380742073059, 1.6087769269943237, 2.1648383140563965, 2.0604288578033447, 1.338661789894104, 1.8750905990600586, 0.8434805274009705, 1.226585030555725, 2.3860201835632324, 2.00657057762146, 1.6817965507507324, 2.3533613681793213, 2.315629243850708, 2.6474545001983643, 1.5313364267349243, 1.8773760795593262, 1.4333877563476562, 1.0445914268493652, 2.416073799133301, 2.807805299758911, 1.7542517185211182, 1.7569174766540527, 1.1008716821670532, 1.3866180181503296, 1.3493404388427734, 1.752619743347168, 1.5931545495986938, 1.2254912853240967, 1.159575343132019, 2.34074330329895, 1.3439210653305054, 2.0377249717712402, 2.1328392028808594, 1.2812942266464233, 1.2673825025558472, 1.4004780054092407, 2.260181427001953, 1.099254846572876, 2.144312858581543, 2.2438690662384033, 1.3856011629104614, 2.8029987812042236, 1.7449908256530762, 1.9722145795822144, 1.8963106870651245, 1.2681825160980225, 1.6825764179229736, 1.7661831378936768, 2.2772703170776367, 2.3254659175872803, 1.6032614707946777, 2.7128071784973145, 0.949644923210144, 1.921028733253479, 1.9253343343734741, 1.538041353225708, 1.0734107494354248, 1.9769494533538818, 1.4885765314102173, 1.2798023223876953, 1.3980680704116821, 2.576209306716919, 1.2122982740402222, 2.5679092407226562, 1.763486623764038, 0.9388672709465027, 1.368211030960083, 1.8555611371994019, 1.5378625392913818, 1.8858338594436646, 2.4717626571655273, 1.4284101724624634, 1.4772003889083862, 1.6679378747940063, 1.5044605731964111, 1.7527885437011719, 1.6439757347106934, 1.0583852529525757, 1.613696813583374, 1.6977171897888184, 2.468937397003174, 1.1331710815429688, 1.0260725021362305, 1.5971035957336426, 1.2358261346817017, 1.9482301473617554, 1.5147827863693237, 1.7893694639205933, 1.068899154663086, 1.315950632095337, 1.2851676940917969, 1.2882564067840576, 1.9414068460464478, 1.9951756000518799, 2.053377389907837, 1.2083407640457153, 2.050269603729248, 1.392210602760315, 2.0615811347961426, 1.6860809326171875, 1.3698220252990723, 1.4833561182022095, 1.494911789894104, 2.0198957920074463, 1.8320919275283813, 1.571858286857605, 1.7631295919418335, 1.1436715126037598, 1.4809963703155518, 2.2581987380981445, 1.7002003192901611, 2.3142828941345215, 1.4982099533081055, 1.551763892173767, 1.1349390745162964, 1.5424861907958984, 2.4940624237060547, 1.053806185722351, 1.9634815454483032, 1.4326908588409424, 1.6877920627593994, 1.8669013977050781, 1.8155320882797241, 1.6194170713424683, 1.6337326765060425, 0.7016921043395996, 1.5451246500015259, 1.6207542419433594, 2.4835867881774902, 1.1283824443817139, 2.1152942180633545, 2.429133653640747, 1.4265612363815308, 2.0935182571411133, 1.407257080078125, 2.1070446968078613, 1.4527465105056763, 2.1870105266571045, 1.8196369409561157, 2.1643571853637695, 0.6399149894714355, 1.2752043008804321, 1.3652490377426147, 2.3338229656219482, 1.210020661354065, 2.3941214084625244, 1.6499266624450684, 2.186934232711792, 1.1389575004577637, 0.7492508292198181, 1.9011629819869995, 1.133769154548645, 1.519136667251587, 1.7809652090072632, 1.6037282943725586, 2.0571141242980957, 1.6806392669677734, 1.0698574781417847, 1.8495832681655884, 1.5630844831466675, 1.1652494668960571, 1.3336374759674072, 1.3350340127944946, 2.297494649887085, 1.189267873764038, 1.07988703250885, 1.8448116779327393, 2.479095458984375, 1.88909113407135, 2.0739784240722656, 2.141979455947876, 1.3480421304702759, 1.5560178756713867, 1.738852858543396, 2.0198922157287598, 1.2913318872451782, 1.1566038131713867, 1.571191668510437, 1.6084537506103516, 1.5831069946289062, 1.8332926034927368, 1.658494472503662, 1.4251813888549805, 1.4719988107681274, 1.8396902084350586, 1.9493956565856934, 2.394822597503662, 1.7194674015045166, 1.7567929029464722, 1.5795944929122925, 2.0814332962036133, 1.784043788909912, 2.6989541053771973, 1.4977096319198608, 2.329681158065796, 1.4416296482086182, 2.0379281044006348, 1.363549828529358, 1.8482385873794556, 1.163560152053833, 1.5395373106002808, 1.0671374797821045, 1.751534104347229, 1.6381876468658447, 1.556892991065979, 1.4339302778244019, 1.5335590839385986, 1.742820382118225, 1.8370217084884644, 1.7720180749893188, 2.5320167541503906, 1.6019325256347656, 1.8909918069839478, 1.7854760885238647, 1.101849913597107, 1.1853947639465332, 1.260554313659668, 1.585771918296814, 2.582148313522339, 2.0250487327575684, 2.2546091079711914, 1.3230739831924438, 2.347787380218506, 1.3399015665054321, 2.041578531265259, 2.2285377979278564, 1.7348377704620361, 1.2808904647827148, 2.1147000789642334, 2.21115779876709, 1.7520294189453125, 1.9791185855865479, 2.2580461502075195, 2.135577440261841, 1.240663766860962, 2.807835102081299, 2.5445497035980225, 0.7246810793876648, 1.6466301679611206, 1.4504040479660034, 3.2613842487335205, 2.2175419330596924, 1.6565933227539062, 1.5815702676773071, 3.1156280040740967, 1.5392452478408813, 1.7299686670303345, 1.4297987222671509, 1.2413833141326904, 2.233072280883789, 1.2803611755371094, 2.091364622116089, 2.120438575744629, 2.0844786167144775, 1.5460067987442017, 1.165419578552246, 1.722418189048767, 2.4649710655212402, 1.8696132898330688, 1.4359132051467896, 1.243924856185913, 1.2192111015319824, 1.8469877243041992, 1.6387722492218018, 1.6863435506820679, 1.532210350036621, 2.403730630874634, 1.7867627143859863, 1.4871078729629517, 1.610878825187683, 1.870394229888916, 1.5590234994888306, 1.7943613529205322, 2.158165454864502, 1.0390052795410156, 172.6729278564453, 73.94866943359375, 152.26959228515625, 113.5290298461914, 295.1939697265625, 145.50311279296875, 94.94593811035156, 103.85050201416016, 121.88851928710938, 34.25295639038086, 127.36588287353516, 95.77468872070312, 200.20726013183594, 203.4638671875, 169.0010528564453, 96.58074951171875, 45.23577880859375, 46.60586166381836, 126.78558349609375, 124.30765533447266, 36.105712890625, 30.795568466186523, 314.0473937988281, 83.88460540771484, 65.16867065429688, 82.07231903076172, 100.4275894165039, 32.23382568359375, 38.30605697631836, 432.9583740234375, 142.0115966796875, 40.549991607666016, 134.22775268554688, 63.41413116455078, 304.770263671875, 244.1005859375, 26.80096435546875, 266.8006286621094, 45.18695068359375, 58.32363510131836, 243.3060302734375, 112.17889404296875, 238.10012817382812, 43.38977813720703, 171.2904052734375, 109.26128387451172, 122.74628448486328, 326.58831787109375, 111.87515258789062, 30.426151275634766, 54.87612533569336, 125.07866668701172, 191.1793975830078, 233.035888671875, 185.654296875, 144.74917602539062, 98.29097747802734, 86.79056549072266, 261.2305908203125, 61.44884490966797, 43.43695068359375, 61.8034782409668, 127.08223724365234, 109.79315185546875, 88.69963073730469, 184.1231231689453, 41.53164291381836, 197.2085723876953, 53.93098449707031, 86.63191223144531, 173.73294067382812, 166.57254028320312, 144.73399353027344, 25.53333282470703, 141.739013671875, 78.89238739013672, 178.3291778564453, 369.7820129394531, 88.32154083251953, 107.55083465576172, 69.89649200439453, 189.52105712890625, 81.26841735839844, 165.4915771484375, 204.7067108154297, 151.2561798095703, 133.34878540039062, 132.64828491210938, 85.8369140625, 149.54307556152344, 73.77996063232422, 128.13873291015625, 152.43972778320312, 185.60400390625, 57.58408737182617, 137.26416015625, 235.61721801757812, 143.005615234375, 225.36058044433594, 238.7109375, 135.1246337890625, 22.04278564453125, 63.489192962646484, 70.28617858886719, 225.50213623046875, 270.48406982421875, 55.8829345703125, 76.6187744140625, 346.2091979980469, 172.98422241210938, 102.09491729736328, 137.12245178222656, 123.78553771972656, 123.720458984375, 151.1627655029297, 216.18136596679688, 164.81358337402344, 118.7044677734375, 119.9638671875, 43.324520111083984, 83.474853515625, 121.32583618164062, 91.92630767822266, 23.9425048828125, 92.91960906982422, 59.3330078125, 65.56466674804688, 179.1962890625, 32.05035400390625, 237.97511291503906, 169.94094848632812, 221.68614196777344, 169.4998016357422, 49.1907958984375, 158.1286163330078, 87.89529418945312, 74.87855529785156, 32.308837890625, 33.78564453125, 229.7459716796875, 115.534423828125, 30.37628173828125, 155.826171875, 79.6756591796875, 29.03173828125, 31.62798309326172, 211.2426300048828, 152.46124267578125, 184.69349670410156, 45.1069221496582, 29.906888961791992, 147.40296936035156, 171.88694763183594, 182.35411071777344, 155.23202514648438, 112.6662368774414, 235.08135986328125, 90.38980102539062, 100.9468994140625, 81.80877685546875, 68.00543975830078, 68.95159912109375, 123.84683227539062, 190.95968627929688, 54.65957260131836, 192.5142364501953, 103.20263671875, 52.96435546875, 212.49632263183594, 148.3597869873047, 153.62266540527344, 249.3271026611328, 40.14178466796875, 290.791015625, 140.31109619140625, 81.4067611694336, 104.07086944580078, 99.78345489501953, 180.1949920654297, 204.90252685546875, 186.9129638671875, 40.470306396484375, 422.9887390136719, 263.8895568847656, 34.866058349609375, 96.9417724609375, 250.92149353027344, 50.727684020996094, 85.5447998046875, 158.84706115722656, 182.5733184814453, 132.46153259277344, 143.0830841064453, 201.4051055908203, 277.2629089355469, 167.2938995361328, 248.80694580078125, 235.14308166503906, 98.63177490234375, 94.360107421875, 141.55039978027344, 70.82364654541016, 59.960487365722656, 319.39520263671875, 46.11618423461914, 104.92048645019531, 174.10411071777344, 125.16507720947266, 215.51190185546875, 77.821044921875, 235.41259765625, 246.3267059326172, 49.3809814453125, 107.85962677001953, 103.10001373291016, 105.56903076171875, 158.6136932373047, 57.264984130859375, 59.00775146484375, 171.5264434814453, 141.64019775390625, 129.614501953125, 101.07058715820312, 121.66268920898438, 357.54913330078125, 187.70172119140625, 321.81707763671875, 214.6667938232422, 234.4141387939453, 86.68644714355469, 281.719482421875, 46.44668960571289, 73.72317504882812, 43.936126708984375, 37.5703125, 64.92912292480469, 136.90321350097656, 116.24822998046875, 37.90101623535156, 296.0921325683594, 308.3858947753906, 58.30329513549805, 140.50418090820312, 104.81832122802734, 128.74761962890625, 87.93505859375, 139.9412841796875, 352.27685546875, 168.50059509277344, 185.57763671875, 90.38628387451172, 226.19842529296875, 158.63671875, 237.5185546875, 125.71646118164062, 38.405517578125, 48.329647064208984, 33.78579330444336, 33.207176208496094, 208.48265075683594, 39.45831298828125, 200.91429138183594, 23.53021240234375, 173.477294921875, 49.22756576538086, 173.03274536132812, 57.45966720581055, 26.89874267578125, 127.63530731201172, 96.3668212890625, 82.23507690429688, 91.63671875, 190.77549743652344, 101.2580337524414, 354.91143798828125, 39.0758056640625, 120.73929595947266, 175.747802734375, 30.5606689453125, 103.25941467285156, 37.98881149291992, 235.1883087158203, 208.3817138671875, 57.48107147216797, 115.12458038330078, 184.7655487060547, 109.09903717041016, 274.0614013671875, 41.71533203125, 67.579833984375, 124.56886291503906, 144.40194702148438, 162.42117309570312, 33.712249755859375, 72.631591796875, 146.23193359375, 150.7338104248047, 33.14715576171875, 29.2294921875, 224.7122802734375, 3.2297680377960205, 2.3888864517211914, 3.065359354019165, 2.4669694900512695, 3.0235073566436768, 2.0951340198516846, 1.8101776838302612, 3.561129570007324, 2.3772671222686768, 2.649083137512207, 2.1820993423461914, 2.0924227237701416, 1.823172926902771, 2.311249017715454, 3.3548083305358887, 3.3247501850128174, 3.047025680541992, 3.1173176765441895, 2.9097893238067627, 1.666193962097168, 3.574578285217285, 2.806692361831665, 1.8733243942260742, 2.045496940612793, 2.2622499465942383, 3.1700637340545654, 1.2249561548233032, 2.61238431930542, 2.8854763507843018, 3.421473503112793, 1.932442545890808, 1.9138611555099487, 2.2804901599884033, 2.925605058670044, 1.7939754724502563, 2.1866137981414795, 2.205415964126587, 1.9921468496322632, 2.6501476764678955, 2.617849349975586, 2.101670980453491, 3.1101062297821045, 3.2351560592651367, 1.7194762229919434, 2.498814582824707, 2.4943971633911133, 2.5931396484375, 1.5036019086837769, 2.7401440143585205, 2.1699821949005127, 2.697434663772583, 2.6960408687591553, 2.721083879470825, 3.5124006271362305, 2.0462276935577393, 2.742072105407715, 2.0656840801239014, 2.3041255474090576, 4.1531291007995605, 2.360745429992676, 2.729961395263672, 3.0231120586395264, 1.1485224962234497, 1.6582772731781006, 2.797711133956909, 3.4579784870147705, 2.107186794281006, 2.393296241760254, 2.1371283531188965, 2.7379112243652344, 2.3907079696655273, 3.232661247253418, 3.476109504699707, 2.9774718284606934, 2.3369977474212646, 1.7897591590881348, 3.0457751750946045, 3.460516929626465, 3.0851407051086426, 2.942694664001465, 1.96821129322052, 1.7909024953842163, 1.5644168853759766, 2.9347259998321533, 3.058795213699341, 3.2454404830932617, 3.070021390914917, 2.384272575378418, 2.73478627204895, 2.333338499069214, 3.8879106044769287, 2.769854784011841, 3.2338016033172607, 1.7004835605621338, 2.2784764766693115, 1.8795576095581055, 3.1373565196990967, 2.0523858070373535, 1.7365930080413818, 3.0456600189208984, 3.5107603073120117, 2.714653253555298, 2.454110860824585, 1.9408413171768188, 2.923907518386841, 3.023993730545044, 4.0133771896362305, 1.184992790222168, 2.0235912799835205, 2.0584325790405273, 3.435397148132324, 2.551684617996216, 3.2672276496887207, 1.9493615627288818, 2.851933479309082, 3.0021276473999023, 3.061711311340332, 2.305150032043457, 1.8953094482421875, 2.9183266162872314, 3.5738964080810547, 4.5472917556762695, 2.1604316234588623, 2.4591827392578125, 2.486887216567993, 2.934088706970215, 2.389010190963745, 1.6078071594238281, 2.20732045173645, 2.828200101852417, 2.932239055633545, 3.681940793991089, 2.649404287338257, 1.7665929794311523, 3.1540615558624268, 2.9708378314971924, 3.7049381732940674, 2.1876726150512695, 3.4461758136749268, 2.3171868324279785, 1.2132372856140137, 2.933142900466919, 2.582537889480591, 2.6955864429473877, 3.0546085834503174, 2.4562768936157227, 3.22615909576416, 2.3475091457366943, 1.7324142456054688, 1.8399873971939087, 1.976602554321289, 2.3782832622528076, 2.7178966999053955, 2.401169776916504, 1.9038686752319336, 2.4165029525756836, 3.176715135574341, 2.7247228622436523, 2.511312484741211, 1.8942251205444336, 2.5826220512390137, 2.6296944618225098, 2.38135027885437, 2.1026010513305664, 1.4292916059494019, 2.7734832763671875, 2.366053342819214, 1.9977445602416992, 2.647972583770752, 2.116691827774048, 2.5128014087677, 3.8812742233276367, 2.6949150562286377, 2.954861879348755, 1.7361187934875488, 1.7563064098358154, 1.7618954181671143, 2.7643158435821533, 1.913819432258606, 2.1599743366241455, 2.8379411697387695, 2.114518404006958, 1.8045697212219238, 2.923093795776367, 2.0942277908325195, 2.367041826248169, 3.1271753311157227, 3.322657585144043, 2.783020257949829, 3.3095273971557617, 3.833441734313965, 3.0074968338012695, 1.595076560974121, 3.93186092376709, 1.3347200155258179, 3.170943021774292, 1.5733437538146973, 2.4928946495056152, 2.1077463626861572, 1.676147699356079, 3.2354748249053955, 2.172107219696045, 1.4926575422286987, 1.7876657247543335, 2.03621244430542, 3.213369607925415, 2.615673780441284, 3.356451988220215, 2.8229916095733643, 2.4579060077667236, 2.4544856548309326, 2.492790460586548, 2.3798394203186035, 2.5761992931365967, 2.936171293258667, 2.9711639881134033, 1.5109525918960571, 2.403048276901245, 1.5660256147384644, 3.05900502204895, 2.880977153778076, 2.970611572265625, 2.9325239658355713, 2.8685314655303955, 2.8179314136505127, 1.9892616271972656, 2.0180177688598633, 3.2618954181671143, 2.8764257431030273, 2.4496569633483887, 1.6320525407791138, 2.630387544631958, 3.2434511184692383, 2.797367811203003, 2.972766399383545, 2.434915781021118, 2.5080134868621826, 3.1465775966644287, 2.191957950592041, 3.3918027877807617, 3.1469192504882812, 3.14235520362854, 2.7187530994415283, 2.3067681789398193, 1.5389978885650635, 3.114753246307373, 1.6091406345367432, 2.52858829498291, 2.4324421882629395, 1.690010905265808, 2.4845314025878906, 2.0598394870758057, 3.3073766231536865, 1.5290616750717163, 2.0982351303100586, 2.3485424518585205, 2.3005306720733643, 3.376718044281006, 2.206648588180542, 3.1770622730255127, 1.4481616020202637, 2.8672289848327637, 2.322504758834839, 3.730597496032715, 2.928945541381836, 1.566267967224121, 1.8097410202026367, 3.6799778938293457, 3.6266167163848877, 4.1775970458984375, 1.6962631940841675, 3.375725269317627, 2.874943733215332, 2.881743907928467, 2.5096921920776367, 1.521710991859436, 2.375805616378784, 3.3235771656036377, 2.0509274005889893, 2.3817150592803955, 1.929378867149353, 2.29757022857666, 3.7286479473114014, 3.0551273822784424, 1.5895050764083862, 2.107327938079834, 1.6152318716049194, 1.4411954879760742, 2.81681752204895, 1.9665212631225586, 2.0131125450134277, 2.1574974060058594, 2.1784982681274414, 1.7370742559432983, 2.476214647293091, 2.9439117908477783, 2.06894588470459, 2.457308530807495, 2.0716981887817383, 1.704836130142212, 0.1461595743894577, 0.23945076763629913, 0.25126054883003235, 0.13428185880184174, 0.17908184230327606, 0.17876434326171875, 0.18718862533569336, 0.1979716569185257, 0.18318139016628265, 0.1491023153066635, 0.22321200370788574, 0.1623896062374115, 0.1649935096502304, 0.17730966210365295, 0.20219938457012177, 0.13633345067501068, 0.1390930861234665, 0.2272651642560959, 0.16433162987232208, 0.25873199105262756, 0.2329307496547699, 0.14266787469387054, 0.13771145045757294, 0.1626766324043274, 0.22139672935009003, 0.1524016559123993, 0.20124244689941406, 0.2395421713590622, 0.25449129939079285, 0.18766982853412628, 0.19966357946395874, 0.14327628910541534, 0.18217484652996063, 0.21158519387245178, 0.2687559723854065, 0.2359689325094223, 0.27733176946640015, 0.12204280495643616, 0.18895088136196136, 0.1770649254322052, 0.21965499222278595, 0.1717190444469452, 0.19700908660888672, 0.15318232774734497, 0.18200035393238068, 0.16170364618301392, 0.20048272609710693, 0.20315344631671906, 0.1908320188522339, 0.19691598415374756, 0.12436238676309586, 0.22266632318496704, 0.2503364384174347, 0.15469539165496826, 0.263944536447525, 0.1444268375635147, 0.22173678874969482, 0.20285402238368988, 0.2253568172454834, 0.16480495035648346, 0.19957631826400757, 0.19190619885921478, 0.19910775125026703, 0.24309155344963074, 0.2593788802623749, 0.11721602827310562, 0.19537170231342316, 0.22093462944030762, 0.20210038125514984, 0.14544939994812012, 0.2033264935016632, 0.15791398286819458, 0.13021090626716614, 0.18770448863506317, 0.1532246619462967, 0.2110450714826584, 0.16720515489578247, 0.1945139318704605, 0.21076831221580505, 0.16471585631370544, 0.13862952589988708, 0.14542929828166962, 0.14511561393737793, 0.19124643504619598, 0.27255308628082275, 0.19727236032485962, 0.14682917296886444, 0.15898165106773376, 0.17624230682849884, 0.2618958353996277, 0.14979729056358337, 0.17448747158050537, 0.19037209451198578, 0.13856780529022217, 0.20863325893878937, 0.18059229850769043, 0.14516761898994446, 0.1870432198047638, 0.21973204612731934, 0.23133158683776855, 0.1834731101989746, 0.18955211341381073, 0.21913498640060425, 0.22273379564285278, 0.21004623174667358, 0.14794021844863892, 0.18652401864528656, 0.16104789078235626, 0.17160020768642426, 0.1510802060365677, 0.21091328561306, 0.10415065288543701, 0.15035338699817657, 0.28947147727012634, 0.16367465257644653, 0.21135644614696503, 0.14271803200244904, 0.1781989187002182, 0.19464904069900513, 0.22418005764484406, 0.1998041421175003, 0.2413748949766159, 0.19942866265773773, 0.17836247384548187, 0.1955091804265976, 0.18275852501392365, 0.25798699259757996, 0.1959361582994461, 0.1772473305463791, 0.1337250918149948, 0.1765449047088623, 0.15345533192157745, 0.2920893132686615, 0.16697677969932556, 0.17993929982185364, 0.2225133776664734, 0.20899291336536407, 0.21105891466140747, 0.20717942714691162, 0.16924312710762024, 0.24433471262454987, 0.20704209804534912, 0.1629553884267807, 0.276278555393219, 0.2188338190317154, 0.2471434473991394, 0.25475752353668213, 0.21838492155075073, 0.24566078186035156, 0.18757018446922302, 0.20999272167682648, 0.1653308868408203, 0.27072685956954956, 0.12982797622680664, 0.13529229164123535, 0.23160046339035034, 0.20729218423366547, 0.23123431205749512, 0.2208683341741562, 0.1345318704843521, 0.2442610114812851, 0.15891680121421814, 0.25846052169799805, 0.2401190847158432, 0.17621783912181854, 0.18408681452274323, 0.1940288543701172, 0.2183203101158142, 0.11947214603424072, 0.2612496614456177, 0.1545531451702118, 0.2409769594669342, 0.17850303649902344, 0.19366633892059326, 0.2137409895658493, 0.18352824449539185, 0.0896167904138565, 0.20877552032470703, 0.2144928276538849, 0.21332406997680664, 0.1711457371711731, 0.14712835848331451, 0.1659182459115982, 0.18056975305080414, 0.24803118407726288, 0.21372531354427338, 0.1814304143190384, 0.17775046825408936, 0.18440818786621094, 0.25020667910575867, 0.1583631932735443, 0.18452434241771698, 0.16764362156391144, 0.1678130328655243, 0.1720246523618698, 0.20548680424690247, 0.09896017611026764, 0.17550204694271088, 0.24545514583587646, 0.2033955305814743, 0.1574234962463379, 0.206953763961792, 0.17445586621761322, 0.16261206567287445, 0.1707434058189392, 0.16845256090164185, 0.25072625279426575, 0.2096218466758728, 0.18894413113594055, 0.22952525317668915, 0.17088773846626282, 0.2158024162054062, 0.22813494503498077, 0.2505039870738983, 0.16663561761379242, 0.20040825009346008, 0.13704104721546173, 0.1989341825246811, 0.19219081103801727, 0.17932994663715363, 0.2752459645271301, 0.1914883553981781, 0.24028253555297852, 0.2539743483066559, 0.15023483335971832, 0.14656829833984375, 0.16601046919822693, 0.21651381254196167, 0.23526304960250854, 0.23535053431987762, 0.15622523427009583, 0.25363069772720337, 0.16773898899555206, 0.20239782333374023, 0.1711307317018509, 0.20429880917072296, 0.21527749300003052, 0.25412556529045105, 0.16315917670726776, 0.21536272764205933, 0.18033786118030548, 0.15665802359580994, 0.12354453653097153, 0.17531424760818481, 0.1902025192975998, 0.16334526240825653, 0.22293242812156677, 0.20586532354354858, 0.17034995555877686, 0.1306777000427246, 0.18348166346549988, 0.16063223779201508, 0.1722024530172348, 0.15069590508937836, 0.23240263760089874, 0.195327490568161, 0.22333616018295288, 0.23912368714809418, 0.1806335747241974, 0.25952768325805664, 0.15497145056724548, 0.21542948484420776, 0.1777658760547638, 0.24689452350139618, 0.24506007134914398, 0.11649763584136963, 0.2266613095998764, 0.1652258336544037, 0.21271222829818726, 0.16355735063552856, 0.15561163425445557, 0.15029685199260712, 0.2536138594150543, 0.2335294932126999, 0.20525777339935303, 0.22980952262878418, 0.18127544224262238, 0.17685845494270325, 0.24645882844924927, 0.19970817863941193, 0.2793557643890381, 0.1858966052532196, 0.21105742454528809, 0.23628970980644226, 0.13578325510025024, 0.16545942425727844, 0.2203420251607895, 0.18657775223255157, 0.2364218533039093, 0.14495137333869934, 0.16466297209262848, 0.22149059176445007, 0.1609870344400406, 0.1410958617925644, 0.20938891172409058, 0.11817922443151474, 0.239074245095253, 0.11572225391864777, 0.15680339932441711, 0.19112825393676758, 3.031996965408325, 1.3690273761749268, 1.9893664121627808, 1.4636940956115723, 2.3788204193115234, 2.534162759780884, 1.963808536529541, 1.720206618309021, 1.8582674264907837, 2.358928680419922, 1.5890334844589233, 2.3539085388183594, 1.395991325378418, 1.4201316833496094, 1.1279791593551636, 2.013622760772705, 1.5953037738800049, 2.2427115440368652, 3.4224178791046143, 1.1268044710159302, 1.2038788795471191, 1.6044714450836182, 1.8347686529159546, 2.1638906002044678, 1.4587739706039429, 1.3450510501861572, 1.2851438522338867, 1.7616525888442993, 1.9512128829956055, 1.87863028049469, 2.674778461456299, 2.3288488388061523, 1.9247872829437256, 1.9588754177093506, 1.6392358541488647, 1.6829191446304321, 2.0877280235290527, 1.9037954807281494, 1.6703981161117554, 1.384177565574646, 1.594238519668579, 2.3464105129241943, 1.478670597076416, 1.8179006576538086, 2.4450490474700928, 1.2424213886260986, 1.2284005880355835, 2.917121171951294, 2.0788137912750244, 1.8494526147842407, 2.0043094158172607, 1.7730963230133057, 2.078385829925537, 1.028012752532959, 1.800493836402893, 0.8767129182815552, 1.0899276733398438, 2.123236894607544, 2.165541887283325, 1.7383276224136353, 1.1688686609268188, 1.7909841537475586, 2.448970317840576, 2.8500397205352783, 2.1321065425872803, 1.5434974431991577, 1.4791665077209473, 1.4976475238800049, 1.8618324995040894, 1.6524877548217773, 1.3965847492218018, 2.0493521690368652, 1.9804253578186035, 0.9955319166183472, 2.0574469566345215, 1.732430100440979, 1.1627888679504395, 1.9155540466308594, 1.6491777896881104, 1.4428787231445312, 1.9965324401855469, 1.9846712350845337, 1.536254644393921, 2.251335620880127, 2.220167636871338, 1.7415659427642822, 2.018164873123169, 1.6893547773361206, 2.8445422649383545, 1.7655209302902222, 1.6626783609390259, 1.0666015148162842, 1.4985485076904297, 2.581672191619873, 1.3322913646697998, 1.2404582500457764, 1.601024866104126, 2.29402756690979, 1.2928273677825928, 1.6114542484283447, 1.5100754499435425, 1.9814573526382446, 1.427384614944458, 1.5620986223220825, 1.022110104560852, 2.0364303588867188, 1.1180845499038696, 1.6121453046798706, 2.0133273601531982, 1.9043344259262085, 1.5647027492523193, 1.3955227136611938, 1.461588740348816, 1.3973095417022705, 1.9906526803970337, 1.5376614332199097, 2.534027099609375, 2.316866159439087, 2.177628517150879, 1.736061930656433, 2.2643849849700928, 1.5990338325500488, 1.9575380086898804, 2.0450692176818848, 1.283980131149292, 1.8585360050201416, 2.032011032104492, 1.3975721597671509, 2.4813694953918457, 2.165215015411377, 2.0395429134368896, 1.8124853372573853, 1.225461721420288, 2.8041322231292725, 1.6345810890197754, 3.665464401245117, 1.1773290634155273, 1.110942006111145, 1.9915269613265991, 1.3383560180664062, 2.3567001819610596, 2.308739185333252, 2.694103956222534, 2.530536651611328, 1.1597838401794434, 1.9539589881896973, 0.739378809928894, 1.0055112838745117, 1.9421132802963257, 2.2708120346069336, 1.8440927267074585, 1.6621427536010742, 1.8483415842056274, 1.331903338432312, 1.5662325620651245, 1.9125465154647827, 1.5613877773284912, 1.5339481830596924, 1.9748666286468506, 1.6891242265701294, 1.4090932607650757, 1.3434667587280273, 2.0087387561798096, 1.7637836933135986, 1.7712637186050415, 1.2357643842697144, 1.6799547672271729, 1.838732361793518, 1.217456579208374, 2.3654375076293945, 1.098939299583435, 1.3044698238372803, 1.4630541801452637, 1.6416475772857666, 2.3417069911956787, 1.2243424654006958, 1.9873336553573608, 1.3031582832336426, 1.7643241882324219, 1.608637809753418, 1.8231607675552368, 1.174304485321045, 2.601274013519287, 1.3715215921401978, 2.058476448059082, 1.4990228414535522, 1.147568941116333, 2.2420599460601807, 1.5280424356460571, 2.0360403060913086, 1.7539324760437012, 2.7755355834960938, 1.2578182220458984, 1.7247806787490845, 1.677485466003418, 1.5097544193267822, 1.99611234664917, 1.9896471500396729, 1.7987886667251587, 1.3906015157699585, 1.4433555603027344, 1.633586049079895, 1.5068222284317017, 1.436547875404358, 1.8490291833877563, 1.937563419342041, 2.681736469268799, 1.7013452053070068, 1.3545423746109009, 1.3614981174468994, 1.1263847351074219, 1.7414785623550415, 1.202162504196167, 2.079509735107422, 2.1878857612609863, 2.0158729553222656, 2.022311210632324, 1.8889604806900024, 2.266605854034424, 2.032165765762329, 1.8746240139007568, 1.6103453636169434, 1.4542019367218018, 2.754558563232422, 2.3152101039886475, 1.252347707748413, 1.4211548566818237, 2.5262808799743652, 1.5183252096176147, 1.9877039194107056, 1.0506763458251953, 1.5714372396469116, 1.6773350238800049, 1.3316576480865479, 1.8246057033538818, 1.752248764038086, 1.419231653213501, 0.665911853313446, 2.365332841873169, 2.029482364654541, 1.3234825134277344, 1.4916332960128784, 2.0255935192108154, 1.2826199531555176, 2.250011444091797, 1.3082064390182495, 1.667893886566162, 2.2039997577667236, 1.7642159461975098, 2.701096773147583, 1.7175688743591309, 2.0938000679016113, 1.1004635095596313, 2.066744327545166, 1.802511215209961, 2.223511219024658, 2.436382293701172, 1.8818793296813965, 1.632632851600647, 1.5019372701644897, 2.048513174057007, 1.8672376871109009, 2.3388452529907227, 1.0326203107833862, 1.7212661504745483, 2.304952621459961, 1.5047043561935425, 1.5282608270645142, 1.249382495880127, 2.9729576110839844, 1.3139632940292358, 1.7576013803482056, 1.5003541707992554, 1.3992855548858643, 1.826971411705017, 1.2204899787902832, 2.141183614730835, 1.7003722190856934, 1.011818528175354, 1.8257158994674683, 1.5220519304275513, 1.1627600193023682, 1.2762771844863892, 1.9300134181976318, 1.8916889429092407, 2.331709146499634, 1.3340110778808594, 1.6971549987792969, 2.0286781787872314, 1.6302590370178223, 2.1453912258148193, 1.504345178604126, 2.488370418548584, 2.173123836517334, 2.0352978706359863, 1.6106328964233398, 1.7349697351455688, 2.2962727546691895, 1.8489837646484375, 2.0652503967285156, 68.830078125, 40.10806655883789, 61.491268157958984, 193.330810546875, 70.63690948486328, 233.96311950683594, 68.44558715820312, 101.15937042236328, 164.0072021484375, 94.03004455566406, 195.97171020507812, 281.5365295410156, 69.57977294921875, 120.23418426513672, 67.11370849609375, 50.28532028198242, 77.57161712646484, 67.93923950195312, 173.615966796875, 294.00518798828125, 92.33265686035156, 82.4287109375, 306.1240234375, 124.90643310546875, 115.59842681884766, 71.11248779296875, 162.42483520507812, 172.64566040039062, 98.19072723388672, 169.99749755859375, 59.58380126953125, 114.5555419921875, 64.50426483154297, 77.5372314453125, 29.688045501708984, 176.1330108642578, 32.8018684387207, 46.10895538330078, 50.614070892333984, 162.0780792236328, 125.64041900634766, 308.3040466308594, 77.36824798583984, 177.67935180664062, 85.00311279296875, 150.40576171875, 181.0706787109375, 84.9222412109375, 70.5820083618164, 87.5830078125, 118.64513397216797, 206.07489013671875, 54.10354232788086, 86.84066009521484, 169.53350830078125, 46.00897216796875, 170.5583953857422, 31.90557861328125, 193.64805603027344, 145.445068359375, 77.04649353027344, 43.970882415771484, 33.5240478515625, 293.0467529296875, 93.13945770263672, 221.50244140625, 37.831912994384766, 203.19395446777344, 57.3226203918457, 179.35018920898438, 66.52408599853516, 190.3016357421875, 123.92103576660156, 105.67082977294922, 42.43374252319336, 186.7855224609375, 144.19140625, 83.3125991821289, 27.800506591796875, 65.69247436523438, 322.7005615234375, 48.1265869140625, 375.4178161621094, 38.124900817871094, 216.88299560546875, 53.66001510620117, 52.220550537109375, 266.9637451171875, 85.1236343383789, 50.47314453125, 156.92051696777344, 133.51821899414062, 161.62245178222656, 370.23541259765625, 97.83441162109375, 142.47100830078125, 75.33963012695312, 245.303466796875, 105.59974670410156, 236.2728271484375, 160.00807189941406, 109.15283203125, 98.773193359375, 167.67442321777344, 40.33269119262695, 100.55484008789062, 185.83251953125, 151.186767578125, 154.56207275390625, 53.043701171875, 94.36817932128906, 169.94366455078125, 45.67729568481445, 59.53440475463867, 121.62020874023438, 219.698486328125, 208.72422790527344, 44.19288635253906, 104.49823760986328, 85.716796875, 62.82525634765625, 110.22445678710938, 97.56644439697266, 180.3365020751953, 164.1190643310547, 55.565185546875, 86.72991943359375, 27.595382690429688, 27.01483154296875, 59.12003707885742, 43.40521240234375, 162.3802490234375, 203.9726104736328, 173.71713256835938, 55.82147216796875, 68.31088256835938, 246.98944091796875, 164.78721618652344, 120.6141357421875, 230.56787109375, 41.319393157958984, 41.30508041381836, 90.7613296508789, 137.3971710205078, 108.24518585205078, 328.10302734375, 210.54754638671875, 85.12583923339844, 203.3950958251953, 36.9405517578125, 118.88188934326172, 154.62832641601562, 277.6094970703125, 41.48577880859375, 212.2963409423828, 175.92160034179688, 323.6983642578125, 161.8566436767578, 69.92119598388672, 86.83454895019531, 138.33856201171875, 83.6989517211914, 104.56332397460938, 29.539579391479492, 275.7251892089844, 128.6409912109375, 43.59931564331055, 42.413124084472656, 280.66815185546875, 92.61429595947266, 140.2880859375, 181.5000762939453, 57.590145111083984, 322.1583557128906, 45.683563232421875, 90.86211395263672, 85.03704833984375, 191.37120056152344, 49.85101318359375, 36.41291809082031, 80.41705322265625, 100.0628890991211, 108.44078063964844, 37.685546875, 59.5511589050293, 86.669677734375, 127.42044830322266, 49.81636047363281, 94.26806640625, 184.39280700683594, 53.63006591796875, 229.20571899414062, 46.77515411376953, 146.0272216796875, 116.34893035888672, 127.78016662597656, 140.1041259765625, 203.7367401123047, 222.88604736328125, 98.14415740966797, 35.813602447509766, 90.795654296875, 191.8137969970703, 189.36936950683594, 39.7822380065918, 85.41500091552734, 229.58700561523438, 38.12799072265625, 42.23421859741211, 236.13206481933594, 156.33822631835938, 167.05364990234375, 33.9874267578125, 250.00946044921875, 184.7798614501953, 129.27554321289062, 129.28565979003906, 77.60745239257812, 113.4390869140625, 203.0297393798828, 78.27456665039062, 174.5072784423828, 194.82655334472656, 136.46331787109375, 210.66233825683594, 50.69287109375, 102.27999877929688, 95.31202697753906, 144.43487548828125, 126.2795181274414, 191.84194946289062, 82.88722229003906, 323.16339111328125, 34.26076889038086, 63.43723678588867, 86.2232666015625, 131.57254028320312, 42.4049072265625, 163.57797241210938, 56.698299407958984, 95.673583984375, 37.323795318603516, 153.2777099609375, 40.697242736816406, 129.5209197998047, 155.75965881347656, 92.58731842041016, 159.28924560546875, 161.62063598632812, 137.36769104003906, 46.630008697509766, 104.72457885742188, 230.55343627929688, 97.29656982421875, 127.58849334716797, 78.10503387451172, 591.1696166992188, 151.5174560546875, 64.4652099609375, 135.23956298828125, 50.17002487182617, 29.032987594604492, 110.99173736572266, 41.22012710571289, 132.81298828125, 229.02395629882812, 72.72710418701172, 98.2386474609375, 30.096282958984375, 153.18275451660156, 107.02427673339844, 176.70199584960938, 47.79876708984375, 73.23553466796875, 148.37939453125, 235.61380004882812, 148.89846801757812, 135.39414978027344, 320.06805419921875, 227.3052520751953, 123.682373046875, 252.0839385986328, 45.8411865234375, 79.3853530883789, 203.7601318359375, 99.91313934326172, 244.32177734375, 180.5899200439453, 37.99711227416992, 32.34524154663086, 195.7256622314453, 125.5353775024414, 84.57125091552734, 135.15391540527344, 189.1129608154297, 74.11590576171875, 67.09085083007812, 243.7670440673828, 62.304832458496094, 74.31640625, 3.5808162689208984, 2.2098171710968018, 2.8714382648468018, 1.6623607873916626, 1.2513980865478516, 1.9931000471115112, 2.0610952377319336, 1.581104040145874, 1.7992477416992188, 2.6307711601257324, 3.1140904426574707, 2.0671234130859375, 1.4604568481445312, 2.5144360065460205, 3.114212989807129, 2.502884864807129, 1.9292020797729492, 2.264350652694702, 2.7478039264678955, 3.0403661727905273, 1.6098368167877197, 2.7897961139678955, 1.8521218299865723, 2.190073251724243, 2.5248537063598633, 1.7345856428146362, 1.9720810651779175, 1.8783921003341675, 2.3406906127929688, 2.2810707092285156, 1.6985214948654175, 1.2881749868392944, 2.01908278465271, 2.4222140312194824, 2.1301002502441406, 3.9029934406280518, 2.4461653232574463, 2.412588357925415, 1.7280120849609375, 2.111845016479492, 4.540591239929199, 1.98000967502594, 3.030440092086792, 1.1077569723129272, 2.237832546234131, 2.9766969680786133, 1.9297112226486206, 1.47733736038208, 3.1864383220672607, 3.0505590438842773, 2.070002555847168, 2.4647092819213867, 2.2603535652160645, 2.2205810546875, 1.693154215812683, 1.296699047088623, 2.393336057662964, 1.4442185163497925, 1.8157256841659546, 3.2620689868927, 2.163727283477783, 1.8059130907058716, 2.48995304107666, 3.7570385932922363, 3.501420259475708, 2.709336519241333, 3.497878313064575, 2.1432619094848633, 2.7078640460968018, 3.5408413410186768, 3.8961381912231445, 2.0039355754852295, 1.7285451889038086, 1.4648809432983398, 2.338042974472046, 2.0654525756835938, 2.395378589630127, 1.9059571027755737, 3.161534309387207, 3.099424362182617, 2.782562255859375, 1.9999008178710938, 2.251321315765381, 3.202936887741089, 2.609614133834839, 3.4549357891082764, 3.523366689682007, 2.646807909011841, 2.6404318809509277, 2.6400580406188965, 2.5816147327423096, 2.2845778465270996, 1.6376879215240479, 2.788958787918091, 2.082526206970215, 2.172734260559082, 2.120522975921631, 2.4583582878112793, 1.9420098066329956, 3.2709362506866455, 2.086534023284912, 3.2715251445770264, 1.564221739768982, 1.588878870010376, 1.9504083395004272, 3.775324583053589, 2.0938634872436523, 2.6527416706085205, 2.1758055686950684, 2.7366597652435303, 2.705669403076172, 2.2224550247192383, 3.406010627746582, 2.617673397064209, 3.8062756061553955, 3.080928087234497, 2.9142675399780273, 1.698409080505371, 2.091491937637329, 3.0953891277313232, 1.7711448669433594, 4.003300666809082, 3.3396928310394287, 2.2804083824157715, 2.2886433601379395, 3.3501315116882324, 1.9944695234298706, 1.7448492050170898, 2.4188411235809326, 1.5663470029830933, 2.741114854812622, 2.957268238067627, 2.2944271564483643, 1.5996341705322266, 3.096684455871582, 3.810903310775757, 2.603411912918091, 2.197828531265259, 1.3560441732406616, 2.26792049407959, 2.0226755142211914, 1.8947882652282715, 3.315830707550049, 3.8191709518432617, 1.9846187829971313, 2.733941078186035, 2.8012914657592773, 1.5375785827636719, 1.528523564338684, 2.678624153137207, 2.7111973762512207, 3.3014039993286133, 2.8192131519317627, 3.8914480209350586, 2.193662166595459, 3.7072644233703613, 2.498995780944824, 3.705690622329712, 3.868781566619873, 3.5422027111053467, 2.095240592956543, 2.0136828422546387, 2.211941957473755, 3.37048077583313, 2.100076913833618, 3.319831132888794, 2.5480411052703857, 2.5978875160217285, 2.848076820373535, 1.3265246152877808, 2.464824676513672, 1.7821314334869385, 1.3116189241409302, 3.665043830871582, 2.7415783405303955, 2.1750869750976562, 2.386185646057129, 1.75458824634552, 2.803635835647583, 2.2018134593963623, 2.2144651412963867, 2.6457574367523193, 1.4961899518966675, 2.4822158813476562, 2.41774845123291, 2.746011257171631, 2.287975311279297, 2.8801121711730957, 3.474447011947632, 2.564202308654785, 1.9300888776779175, 1.8395241498947144, 2.888211250305176, 1.6435974836349487, 2.566647529602051, 1.7469817399978638, 1.524263620376587, 2.0040979385375977, 1.8538638353347778, 1.6522225141525269, 1.7868202924728394, 2.2696828842163086, 2.270366668701172, 2.9092395305633545, 1.841235876083374, 1.3946382999420166, 2.866816759109497, 3.0831780433654785, 1.778908610343933, 2.223067283630371, 2.335517168045044, 2.848567247390747, 2.631221294403076, 1.8605822324752808, 2.7131712436676025, 2.300196409225464, 3.184880256652832, 3.05143666267395, 1.7211931943893433, 1.8281105756759644, 1.4560106992721558, 1.7702105045318604, 2.105813503265381, 3.049140214920044, 2.300198554992676, 3.8225584030151367, 3.3133764266967773, 2.524775505065918, 2.459627866744995, 1.9155328273773193, 2.5846078395843506, 2.5859832763671875, 2.8410463333129883, 2.018141746520996, 1.7875949144363403, 2.2471418380737305, 1.446486473083496, 2.60311222076416, 1.6123151779174805, 2.221991539001465, 4.074962139129639, 2.750669002532959, 2.6704154014587402, 3.831446409225464, 2.6227378845214844, 2.4220972061157227, 2.6849937438964844, 1.659114956855774, 2.8946175575256348, 3.806485176086426, 2.0649824142456055, 1.6376159191131592, 3.011157512664795, 2.163252830505371, 2.5332000255584717, 2.2373669147491455, 2.9082248210906982, 3.157752275466919, 3.2442681789398193, 2.8004791736602783, 1.7349233627319336, 2.6439850330352783, 2.2295949459075928, 1.653090476989746, 1.8680830001831055, 2.128720283508301, 3.48637318611145, 2.194206714630127, 2.596177339553833, 2.2791473865509033, 2.868974447250366, 2.867030382156372, 2.0377111434936523, 2.3156609535217285, 2.814504623413086, 2.5662877559661865, 1.3409470319747925, 2.8882110118865967, 2.479495048522949, 1.6943804025650024, 2.346651792526245, 2.3736467361450195, 2.0290613174438477, 1.775837779045105, 2.413010597229004, 2.1659631729125977, 2.053365707397461, 2.0084152221679688, 3.1602025032043457, 3.525149345397949, 3.3999125957489014, 2.598203182220459, 3.0006420612335205, 1.7824851274490356, 2.762781858444214, 2.9196178913116455, 1.8690710067749023, 3.1818859577178955, 2.7548229694366455, 2.652775764465332, 0.20170195400714874, 0.17413127422332764, 0.20353808999061584, 0.15050074458122253, 0.20268577337265015, 0.2316346913576126, 0.14248692989349365, 0.18266884982585907, 0.25445255637168884, 0.15764790773391724, 0.20220062136650085, 0.13682813942432404, 0.21253079175949097, 0.20047500729560852, 0.1347062587738037, 0.1486879289150238, 0.13419818878173828, 0.12230390310287476, 0.18084679543972015, 0.19669316709041595, 0.20205837488174438, 0.19708310067653656, 0.27791205048561096, 0.2279926985502243, 0.19397327303886414, 0.20507760345935822, 0.15012790262699127, 0.2033030241727829, 0.13895870745182037, 0.19892756640911102, 0.14937633275985718, 0.16321714222431183, 0.11972808837890625, 0.1614580899477005, 0.1340998411178589, 0.22920651733875275, 0.19883355498313904, 0.22673365473747253, 0.20336119830608368, 0.16252239048480988, 0.19478999078273773, 0.20135945081710815, 0.26317933201789856, 0.20812010765075684, 0.2128543108701706, 0.20887517929077148, 0.25232023000717163, 0.24035385251045227, 0.16517873108386993, 0.17554590106010437, 0.1851409673690796, 0.1991959661245346, 0.2121240198612213, 0.26722878217697144, 0.16404956579208374, 0.22557711601257324, 0.19962619245052338, 0.26560917496681213, 0.22243553400039673, 0.22459906339645386, 0.22502735257148743, 0.2454201877117157, 0.17774459719657898, 0.17164123058319092, 0.1268506944179535, 0.16737566888332367, 0.15661776065826416, 0.23582971096038818, 0.22697657346725464, 0.15894152224063873, 0.25073185563087463, 0.20133620500564575, 0.13295018672943115, 0.24459438025951385, 0.18034274876117706, 0.15786497294902802, 0.17268139123916626, 0.16337130963802338, 0.21413083374500275, 0.20457513630390167, 0.1864556521177292, 0.19061915576457977, 0.16090446710586548, 0.22585254907608032, 0.18001504242420197, 0.22846205532550812, 0.25636225938796997, 0.10399007797241211, 0.1595686823129654, 0.17047379910945892, 0.2553817629814148, 0.21586132049560547, 0.22137576341629028, 0.24684280157089233, 0.1848984807729721, 0.23203116655349731, 0.17154212296009064, 0.192422017455101, 0.23483708500862122, 0.2607375979423523, 0.2325761765241623, 0.16442033648490906, 0.2009434998035431, 0.21036292612552643, 0.13436855375766754, 0.15578129887580872, 0.2397259920835495, 0.23020638525485992, 0.10436781495809555, 0.2024577111005783, 0.14801235496997833, 0.2118084728717804, 0.22246916592121124, 0.1862667053937912, 0.14158783853054047, 0.2151709347963333, 0.16131526231765747, 0.18538163602352142, 0.1467130333185196, 0.14952829480171204, 0.1809396892786026, 0.2533624470233917, 0.13647614419460297, 0.12129521369934082, 0.23088225722312927, 0.17566664516925812, 0.21599732339382172, 0.1399935930967331, 0.17662417888641357, 0.16402749717235565, 0.14859378337860107, 0.15815594792366028, 0.1542220115661621, 0.12126477062702179, 0.2312464863061905, 0.14366622269153595, 0.15329165756702423, 0.13081322610378265, 0.19955472648143768, 0.18004314601421356, 0.17317147552967072, 0.16799171268939972, 0.16978223621845245, 0.16336558759212494, 0.19939060509204865, 0.18183261156082153, 0.20394989848136902, 0.14503434300422668, 0.2522179186344147, 0.20337019860744476, 0.22297698259353638, 0.20207026600837708, 0.24821597337722778, 0.18543635308742523, 0.1882937252521515, 0.23167769610881805, 0.09569083899259567, 0.1340186595916748, 0.16170544922351837, 0.26446738839149475, 0.20682480931282043, 0.21457400918006897, 0.16756801307201385, 0.21371503174304962, 0.1951589584350586, 0.20773468911647797, 0.23878474533557892, 0.14691278338432312, 0.22309504449367523, 0.2234162539243698, 0.20729318261146545, 0.1911841481924057, 0.17622949182987213, 0.14990830421447754, 0.23234239220619202, 0.18749089539051056, 0.17817725241184235, 0.20260608196258545, 0.23622934520244598, 0.21524906158447266, 0.24643222987651825, 0.1377609819173813, 0.16944776475429535, 0.1838349550962448, 0.21125195920467377, 0.22464977204799652, 0.2226005345582962, 0.17096853256225586, 0.18110190331935883, 0.15654851496219635, 0.15701410174369812, 0.17471885681152344, 0.15484321117401123, 0.2214563637971878, 0.17406894266605377, 0.16194216907024384, 0.27811649441719055, 0.22505617141723633, 0.2295995056629181, 0.18951378762722015, 0.22948022186756134, 0.2107824683189392, 0.1447390764951706, 0.25922200083732605, 0.1801529973745346, 0.2281503975391388, 0.1923878788948059, 0.17049892246723175, 0.17955134809017181, 0.1966327279806137, 0.12428618967533112, 0.12941761314868927, 0.22468048334121704, 0.2379007637500763, 0.16532599925994873, 0.15740208327770233, 0.20944344997406006, 0.1886051893234253, 0.1591389775276184, 0.1965462863445282, 0.12618543207645416, 0.24830976128578186, 0.1626083105802536, 0.19166028499603271, 0.24024997651576996, 0.18953385949134827, 0.1748446673154831, 0.19205008447170258, 0.1770835518836975, 0.2403208166360855, 0.16864986717700958, 0.1506144255399704, 0.22098438441753387, 0.21122394502162933, 0.20849762856960297, 0.24523226916790009, 0.17541225254535675, 0.18205168843269348, 0.16948989033699036, 0.2127508670091629, 0.24926097691059113, 0.10342970490455627, 0.16616316139698029, 0.12952055037021637, 0.3074643015861511, 0.1469743251800537, 0.24549460411071777, 0.14678743481636047, 0.23186977207660675, 0.19436080753803253, 0.17488475143909454, 0.17485027015209198, 0.2663257420063019, 0.19062252342700958, 0.17719200253486633, 0.18220160901546478, 0.1632457673549652, 0.1412893533706665, 0.20756465196609497, 0.17750592529773712, 0.20742732286453247, 0.2543445825576782, 0.2224515825510025, 0.12274303287267685, 0.18718071281909943, 0.1900637149810791, 0.148505300283432, 0.14477047324180603, 0.20885148644447327, 0.17548835277557373, 0.1892632246017456, 0.22568555176258087, 0.2527584731578827, 0.2176741510629654, 0.19081993401050568, 0.23845899105072021, 0.1315605193376541, 0.14525631070137024, 0.18152396380901337, 0.22298087179660797, 0.23009777069091797, 0.18270529806613922, 0.24284601211547852, 0.21591603755950928, 0.22569140791893005, 0.13020820915699005, 0.18396277725696564, 0.1710103154182434, 0.24799513816833496, 0.23206809163093567, 0.19421367347240448, 0.2018032819032669, 0.15885552763938904, 0.2194536328315735, 0.1794678419828415, 0.18155749142169952, 0.23842638731002808, 0.22044287621974945, 0.19178397953510284, 0.20456576347351074, 2.129749298095703, 2.5824673175811768, 2.3951473236083984, 1.6812717914581299, 1.4175955057144165, 2.1228415966033936, 1.5636461973190308, 1.7034879922866821, 1.6571511030197144, 2.497818946838379, 1.7949919700622559, 2.022188901901245, 1.919663906097412, 1.6026531457901, 2.147876501083374, 1.7658251523971558, 1.202270269393921, 2.2194550037384033, 2.3203608989715576, 0.8037627339363098, 1.9971657991409302, 2.100609302520752, 1.79854154586792, 1.9637413024902344, 1.7684414386749268, 1.6355737447738647, 2.1355671882629395, 1.5126298666000366, 1.7022466659545898, 2.0853946208953857, 1.788191795349121, 1.5686043500900269, 1.9877550601959229, 1.839697241783142, 2.3977768421173096, 1.624580979347229, 2.036212205886841, 2.2180378437042236, 1.700231909751892, 1.4454421997070312, 2.110488176345825, 1.6448478698730469, 0.9097793102264404, 1.6501760482788086, 1.7527825832366943, 1.7576467990875244, 1.6109237670898438, 1.9658393859863281, 1.9600023031234741, 1.9232248067855835, 2.0799520015716553, 1.4206631183624268, 1.1468983888626099, 1.6049267053604126, 1.8334696292877197, 1.3186105489730835, 1.0720858573913574, 1.4736814498901367, 1.481925368309021, 1.5631153583526611, 2.363159656524658, 1.106001853942871, 1.6292803287506104, 2.148468494415283, 1.8552736043930054, 1.413643479347229, 1.2412967681884766, 1.6345770359039307, 1.8827470541000366, 1.235351324081421, 2.2708492279052734, 2.4453489780426025, 1.9708601236343384, 1.4717333316802979, 1.9404789209365845, 1.9102386236190796, 1.2985485792160034, 1.5892165899276733, 2.239823818206787, 2.562638521194458, 1.1080011129379272, 2.047386407852173, 1.4578875303268433, 1.501737356185913, 2.2383031845092773, 1.4481136798858643, 1.6847457885742188, 1.0911657810211182, 1.4455959796905518, 1.4509552717208862, 1.1637476682662964, 1.7951176166534424, 1.088371753692627, 1.1818037033081055, 2.4052417278289795, 2.0993669033050537, 2.2247984409332275, 1.4831358194351196, 2.878767728805542, 2.4888272285461426, 2.567614793777466, 2.2752139568328857, 1.3470726013183594, 2.236267328262329, 2.389054775238037, 1.5444608926773071, 2.882777690887451, 1.9051525592803955, 1.4507486820220947, 1.5825897455215454, 1.4651826620101929, 1.709894061088562, 1.8654530048370361, 1.822452187538147, 1.8556314706802368, 1.240598440170288, 1.993888258934021, 1.8779888153076172, 1.5466234683990479, 1.3646856546401978, 2.0153069496154785, 1.4318838119506836, 1.894775629043579, 1.8697319030761719, 1.997058391571045, 1.5785318613052368, 1.9498484134674072, 2.0894806385040283, 1.2042289972305298, 1.7820119857788086, 1.0881896018981934, 1.871903896331787, 1.2418735027313232, 1.322934865951538, 2.6446635723114014, 1.4267733097076416, 1.3682661056518555, 1.8515161275863647, 2.1319119930267334, 1.5891233682632446, 2.391941547393799, 1.3998959064483643, 2.435298442840576, 1.6689809560775757, 1.4513860940933228, 2.1807262897491455, 2.6568844318389893, 2.1508193016052246, 1.5798994302749634, 1.6560261249542236, 1.5636272430419922, 1.3214226961135864, 1.5925871133804321, 1.567901611328125, 1.2581807374954224, 2.4946184158325195, 2.1286866664886475, 1.9868134260177612, 1.672670841217041, 1.531166911125183, 1.0555611848831177, 1.1112380027770996, 1.4207589626312256, 1.247335433959961, 2.204000473022461, 1.6464647054672241, 2.0402543544769287, 2.2528879642486572, 1.0515201091766357, 2.7221620082855225, 1.9339230060577393, 2.189480781555176, 2.911024808883667, 1.5006771087646484, 2.1132748126983643, 1.8091436624526978, 2.1721203327178955, 1.278617024421692, 1.6894694566726685, 1.8405866622924805, 2.1114771366119385, 1.4068584442138672, 2.3483004570007324, 1.7548143863677979, 1.5520882606506348, 1.9784445762634277, 2.5906810760498047, 1.494209885597229, 2.085447311401367, 1.0000718832015991, 1.8785451650619507, 2.05283260345459, 1.377813696861267, 2.046579122543335, 2.0715510845184326, 1.2883599996566772, 1.6624850034713745, 1.7692205905914307, 1.7979322671890259, 1.7968370914459229, 1.89041006565094, 1.5322227478027344, 2.318477153778076, 2.3642032146453857, 2.230032205581665, 2.0786654949188232, 1.9545836448669434, 1.5025689601898193, 1.4494646787643433, 2.3540730476379395, 1.7136526107788086, 1.963693380355835, 1.4058881998062134, 2.341329574584961, 2.2641184329986572, 1.3130217790603638, 1.6422573328018188, 2.1686813831329346, 1.3228402137756348, 1.9982357025146484, 1.114351749420166, 1.9448426961898804, 2.099076747894287, 1.5677067041397095, 2.150949001312256, 1.8269699811935425, 2.3091626167297363, 2.3992910385131836, 1.6167374849319458, 1.5661958456039429, 0.9153329133987427, 1.5036321878433228, 1.1600526571273804, 2.21633243560791, 1.4870846271514893, 1.2044880390167236, 1.9635305404663086, 1.7003449201583862, 1.5308808088302612, 1.6161025762557983, 2.0424346923828125, 1.334383249282837, 2.2507338523864746, 1.308232069015503, 2.7365779876708984, 1.2178807258605957, 2.027100086212158, 1.9717060327529907, 1.2069549560546875, 1.4405617713928223, 2.0848028659820557, 1.3130924701690674, 2.1706838607788086, 2.1231894493103027, 1.4041694402694702, 1.2999868392944336, 1.3328112363815308, 1.6125118732452393, 1.1289759874343872, 1.7125109434127808, 1.5559231042861938, 1.3086827993392944, 1.2392641305923462, 2.125504970550537, 1.079798698425293, 1.6240441799163818, 1.2969223260879517, 1.4761769771575928, 1.9132829904556274, 0.9837167859077454, 1.7841325998306274, 1.8231836557388306, 1.2420907020568848, 1.3271347284317017, 2.641502618789673, 1.8628051280975342, 1.651423454284668, 2.2136969566345215, 1.455769419670105, 1.9361768960952759, 1.7461638450622559, 2.0347745418548584, 1.9756438732147217, 2.1886038780212402, 1.699662446975708, 1.9133074283599854, 1.736053705215454, 2.8967442512512207, 1.9903494119644165, 1.0864262580871582, 2.4725241661071777, 1.380098581314087, 1.6506202220916748, 1.9668517112731934, 2.105759859085083, 1.8781286478042603, 1.9334670305252075, 1.5214954614639282, 2.6080963611602783, 2.569183349609375, 184.02114868164062, 131.44049072265625, 315.42864990234375, 105.05643463134766, 58.56591796875, 93.154052734375, 96.80580139160156, 56.66592788696289, 384.5328674316406, 255.5272216796875, 78.09776306152344, 251.8095703125, 116.08646392822266, 238.28135681152344, 116.42003631591797, 122.50811004638672, 130.9974365234375, 153.0089569091797, 41.76148986816406, 191.61827087402344, 33.267425537109375, 34.67972183227539, 66.79141235351562, 128.11151123046875, 151.36962890625, 103.67976379394531, 278.4531555175781, 177.4404296875, 547.6859130859375, 55.24456787109375, 103.51974487304688, 171.11007690429688, 58.90618896484375, 66.172607421875, 114.09539794921875, 153.92486572265625, 31.016996383666992, 76.402099609375, 97.90552520751953, 47.49725341796875, 207.08555603027344, 47.77044677734375, 161.70469665527344, 148.95411682128906, 45.30801773071289, 135.32025146484375, 146.8939971923828, 117.46401977539062, 295.9891662597656, 171.2977752685547, 256.0128173828125, 121.6311264038086, 310.0843200683594, 237.21502685546875, 88.32679748535156, 148.02198791503906, 85.02239990234375, 163.30577087402344, 286.721435546875, 272.62860107421875, 269.2821044921875, 179.41751098632812, 111.33901977539062, 313.8723449707031, 61.27471923828125, 57.224002838134766, 54.822265625, 118.3416748046875, 69.0679931640625, 152.4539794921875, 197.2975616455078, 63.2430419921875, 207.66563415527344, 174.38134765625, 87.7769546508789, 84.718017578125, 50.328914642333984, 104.10021209716797, 72.204833984375, 90.9711685180664, 109.74854278564453, 102.87054443359375, 223.790771484375, 125.13529968261719, 240.94444274902344, 134.90191650390625, 32.477081298828125, 88.08615112304688, 171.56137084960938, 148.8460693359375, 222.83917236328125, 278.6952819824219, 39.17474365234375, 71.22259521484375, 50.173828125, 135.0028839111328, 117.42729949951172, 134.61212158203125, 81.29266357421875, 37.32194519042969, 215.4715118408203, 212.09803771972656, 36.586917877197266, 290.0338134765625, 71.23373413085938, 83.49530029296875, 222.63034057617188, 153.19873046875, 103.826904296875, 191.26397705078125, 37.84942626953125, 67.10919952392578, 171.07534790039062, 169.5271453857422, 122.02587890625, 70.65846252441406, 75.39617919921875, 153.8651123046875, 122.56749725341797, 327.4263916015625, 208.6599884033203, 199.0474395751953, 53.960540771484375, 99.6792984008789, 173.8132781982422, 36.1693115234375, 327.7381896972656, 151.5159149169922, 213.7558135986328, 76.69294738769531, 151.19248962402344, 178.9970703125, 57.942195892333984, 143.4188690185547, 216.2284393310547, 148.38134765625, 83.44710540771484, 193.10208129882812, 181.0258026123047, 307.25164794921875, 137.45655822753906, 211.44561767578125, 211.46502685546875, 98.02959442138672, 257.1192626953125, 88.03935241699219, 265.4317626953125, 68.23640441894531, 47.84710693359375, 76.42974090576172, 78.23333740234375, 169.5906982421875, 115.85128784179688, 104.68280029296875, 199.0747833251953, 263.6562194824219, 81.53704833984375, 63.51092529296875, 131.62937927246094, 156.93359375, 46.6138916015625, 52.74543380737305, 292.2104187011719, 65.14614868164062, 49.69223403930664, 41.57659912109375, 129.11627197265625, 47.44287109375, 91.84539794921875, 84.28752136230469, 58.148738861083984, 188.74853515625, 181.9324188232422, 136.47662353515625, 95.55155181884766, 148.32769775390625, 267.45172119140625, 245.7476043701172, 119.28887176513672, 73.6224136352539, 42.401824951171875, 88.91082000732422, 53.97023391723633, 157.9474639892578, 53.39894104003906, 38.60540008544922, 190.31114196777344, 65.54219818115234, 84.07568359375, 50.62411117553711, 38.97848129272461, 214.7050323486328, 25.1837158203125, 139.10452270507812, 146.5167694091797, 41.74651336669922, 103.773193359375, 119.05962371826172, 43.6090087890625, 221.1630096435547, 235.15640258789062, 313.0203857421875, 204.9272003173828, 46.15071105957031, 87.05026245117188, 80.9227066040039, 346.2210998535156, 254.579833984375, 119.5654296875, 227.2835693359375, 111.49279022216797, 99.72967529296875, 260.3271789550781, 201.2003936767578, 164.36410522460938, 163.60427856445312, 242.45050048828125, 75.4019775390625, 227.5658721923828, 266.4283447265625, 139.05062866210938, 108.3236083984375, 160.09600830078125, 154.76229858398438, 191.1473846435547, 60.865535736083984, 124.48667907714844, 178.9619140625, 66.87721252441406, 97.2762451171875, 115.29805755615234, 182.23370361328125, 133.8572998046875, 163.97640991210938, 174.2218780517578, 265.4845886230469, 146.09458923339844, 25.919130325317383, 43.387901306152344, 48.24578857421875, 169.7373809814453, 147.73773193359375, 160.24639892578125, 136.5052947998047, 58.193660736083984, 186.88734436035156, 290.2032470703125, 56.67689514160156, 154.0661163330078, 145.9936065673828, 51.7593994140625, 45.226318359375, 93.86260223388672, 62.30169677734375, 46.69563293457031, 123.89824676513672, 50.232513427734375, 90.59142303466797, 61.463279724121094, 37.2181396484375, 181.2993927001953, 275.0155334472656, 165.26097106933594, 148.17385864257812, 247.5483856201172, 146.00942993164062, 154.9674530029297, 243.09432983398438, 198.8251190185547, 76.848876953125, 52.30218505859375, 41.58779525756836, 115.10112762451172, 151.64385986328125, 135.21746826171875, 60.52783203125, 191.5029296875, 84.14095306396484, 33.008277893066406, 129.9920654296875, 41.514892578125, 176.90823364257812, 31.0474853515625, 166.7704315185547, 283.29046630859375, 217.2889404296875, 34.615745544433594, 64.99590301513672, 33.09969711303711, 58.11415481567383, 113.96495819091797, 155.880615234375, 93.87468719482422, 278.09283447265625, 104.2391586303711, 57.07953643798828, 79.14742279052734, 114.634521484375, 133.14263916015625, 129.16387939453125, 2.3122034072875977, 1.3759822845458984, 1.9960012435913086, 2.486743211746216, 1.8069199323654175, 1.7642680406570435, 2.948406219482422, 3.1468725204467773, 2.153449058532715, 1.686909556388855, 2.0227108001708984, 3.1471104621887207, 1.7774648666381836, 1.926216959953308, 1.4250974655151367, 1.6774441003799438, 1.8798562288284302, 3.193132162094116, 2.245971441268921, 2.642228126525879, 2.008265733718872, 3.315727710723877, 3.457294225692749, 2.1907448768615723, 2.00832462310791, 3.139091968536377, 2.8010475635528564, 2.5255818367004395, 2.5199849605560303, 3.2104110717773438, 2.541437864303589, 3.2758493423461914, 1.8311752080917358, 3.5861504077911377, 2.210989475250244, 2.1971681118011475, 3.416530132293701, 3.1150448322296143, 2.513300895690918, 3.7400524616241455, 1.8873385190963745, 3.2351090908050537, 2.772632360458374, 2.7624785900115967, 2.323307991027832, 2.554919958114624, 2.479245185852051, 2.111820936203003, 1.5625312328338623, 2.023739814758301, 3.5321779251098633, 1.9881426095962524, 3.146515130996704, 3.2165708541870117, 2.1265907287597656, 3.703254222869873, 2.507145881652832, 2.6708972454071045, 1.9879484176635742, 2.656636953353882, 2.323981285095215, 1.755077600479126, 2.907099485397339, 3.3869378566741943, 3.7661349773406982, 1.9783530235290527, 1.7544889450073242, 2.277555227279663, 1.8983268737792969, 3.1864733695983887, 2.491596221923828, 1.8571807146072388, 2.5334548950195312, 2.061558723449707, 3.2561798095703125, 2.027195930480957, 2.6239399909973145, 1.8797234296798706, 2.001420736312866, 2.9559261798858643, 2.038022994995117, 1.702595591545105, 3.9100780487060547, 2.802901268005371, 1.2365773916244507, 1.7597016096115112, 2.5851986408233643, 2.2173051834106445, 1.6763067245483398, 2.3099260330200195, 1.9651769399642944, 2.1992764472961426, 2.1524112224578857, 2.9491357803344727, 2.063478708267212, 2.4104909896850586, 2.307157039642334, 3.641069173812866, 2.983381986618042, 1.9955854415893555, 2.940702438354492, 2.3912367820739746, 2.684605598449707, 3.1229794025421143, 1.8984578847885132, 2.6695778369903564, 1.4883090257644653, 1.962577223777771, 1.370289921760559, 2.4972569942474365, 2.1323981285095215, 1.738173484802246, 2.9800329208374023, 3.126556873321533, 2.1265065670013428, 2.0683999061584473, 2.366551637649536, 2.397669553756714, 1.9935463666915894, 3.1782805919647217, 1.6692304611206055, 2.7016398906707764, 2.130009651184082, 2.607945442199707, 2.8586649894714355, 3.9799373149871826, 2.4137065410614014, 1.7120361328125, 2.33853816986084, 1.9912728071212769, 2.672760486602783, 2.3996598720550537, 1.7050487995147705, 3.9459469318389893, 2.085322618484497, 1.6174813508987427, 2.661785840988159, 2.198457717895508, 1.682497501373291, 3.18229603767395, 2.597363233566284, 2.460042715072632, 2.432602882385254, 3.6090147495269775, 2.05794620513916, 2.998896360397339, 2.5678298473358154, 2.6778194904327393, 2.0271120071411133, 2.724224805831909, 3.1747944355010986, 2.2182977199554443, 2.3500967025756836, 2.701566219329834, 2.1546552181243896, 1.9390381574630737, 1.263253092765808, 1.9548064470291138, 1.408339500427246, 3.0604848861694336, 2.9112517833709717, 2.2614798545837402, 3.159132719039917, 2.613204002380371, 2.5968379974365234, 1.8452249765396118, 2.8732147216796875, 2.8254640102386475, 2.3496429920196533, 3.0545666217803955, 3.3977291584014893, 3.247235059738159, 1.914581298828125, 2.2599804401397705, 2.4825196266174316, 2.4197094440460205, 2.2841787338256836, 1.9530553817749023, 3.0751733779907227, 3.1648895740509033, 3.1117372512817383, 2.4918031692504883, 3.4033305644989014, 3.71567440032959, 3.351282835006714, 2.813952684402466, 2.397233009338379, 2.597412109375, 2.7579896450042725, 1.9196654558181763, 2.863179922103882, 1.99189293384552, 2.94958233833313, 2.5529606342315674, 2.222426414489746, 2.580174446105957, 1.7639636993408203, 3.4995813369750977, 1.4444401264190674, 1.6604344844818115, 3.10044002532959, 2.996800422668457, 2.331286668777466, 2.915351152420044, 1.5426511764526367, 1.8909310102462769, 3.183171510696411, 3.0316574573516846, 2.6032707691192627, 1.9821633100509644, 2.0264394283294678, 1.5982674360275269, 2.5283021926879883, 2.415003538131714, 1.695985198020935, 2.864813804626465, 2.8534252643585205, 1.8278030157089233, 2.464627265930176, 1.8517621755599976, 3.2024142742156982, 2.143110513687134, 2.3104782104492188, 3.550279378890991, 2.1856396198272705, 3.5057811737060547, 2.7527360916137695, 2.021678924560547, 2.865307569503784, 2.1664938926696777, 2.3947343826293945, 1.5172148942947388, 3.3314924240112305, 3.258925199508667, 3.0653305053710938, 2.3745529651641846, 2.6060497760772705, 2.860308885574341, 2.394379138946533, 2.9663608074188232, 3.1874988079071045, 3.0849292278289795, 1.7332834005355835, 1.1560372114181519, 2.937544584274292, 3.567538261413574, 3.71940541267395, 2.374903440475464, 2.375905990600586, 2.5258078575134277, 2.927569627761841, 2.428277015686035, 1.9868630170822144, 3.1533443927764893, 1.6029669046401978, 1.4308329820632935, 1.8152166604995728, 3.6895382404327393, 1.8692294359207153, 3.325356960296631, 3.1219470500946045, 2.354012966156006, 2.852343797683716, 3.4737932682037354, 2.2404720783233643, 3.357569694519043, 2.548794746398926, 2.578688621520996, 2.637432813644409, 2.74459171295166, 2.7203285694122314, 3.479841947555542, 2.629693031311035, 2.448835849761963, 2.00296688079834, 2.6453471183776855, 2.6854665279388428, 2.3820064067840576, 2.21572208404541, 2.8692431449890137, 3.888941526412964, 2.9770617485046387, 1.2858610153198242, 2.589677095413208, 2.3672494888305664, 2.3152618408203125, 2.1195149421691895, 1.5247849225997925, 2.95851993560791, 2.7131898403167725, 1.682343602180481, 1.2807302474975586, 1.7876317501068115, 1.7118886709213257, 2.543229103088379, 1.4616985321044922, 2.7556164264678955, 1.9656041860580444, 1.731806755065918, 1.7546502351760864, 0.22671669721603394, 0.20727242529392242, 0.22395293414592743, 0.18495875597000122, 0.24972563982009888, 0.14359234273433685, 0.1891038417816162, 0.2419964224100113, 0.18527020514011383, 0.212164506316185, 0.25704795122146606, 0.20599719882011414, 0.19542132318019867, 0.12438733875751495, 0.17104041576385498, 0.21106667816638947, 0.2594195604324341, 0.18106257915496826, 0.2405359148979187, 0.16283981502056122, 0.3085147440433502, 0.14394481480121613, 0.15293852984905243, 0.1818801909685135, 0.2097388356924057, 0.24455194175243378, 0.2643734812736511, 0.1674838811159134, 0.26301661133766174, 0.222508504986763, 0.23798690736293793, 0.2147364616394043, 0.17210112512111664, 0.21463622152805328, 0.147428959608078, 0.1724981814622879, 0.1368250995874405, 0.20831550657749176, 0.24376410245895386, 0.13842393457889557, 0.151786208152771, 0.19979305565357208, 0.2069893479347229, 0.22995826601982117, 0.14135922491550446, 0.1911461353302002, 0.19298651814460754, 0.23907470703125, 0.15273642539978027, 0.20811286568641663, 0.16453517973423004, 0.20802199840545654, 0.12970933318138123, 0.15288382768630981, 0.1432502567768097, 0.16471625864505768, 0.10340753942728043, 0.20189929008483887, 0.18773680925369263, 0.22352086007595062, 0.20591235160827637, 0.1576218605041504, 0.2490806132555008, 0.15775954723358154, 0.26462772488594055, 0.18302474915981293, 0.22310714423656464, 0.14522160589694977, 0.22620944678783417, 0.24189196527004242, 0.1855699121952057, 0.1430140882730484, 0.20743396878242493, 0.29077309370040894, 0.16121791303157806, 0.17222675681114197, 0.1343502402305603, 0.21071740984916687, 0.18871909379959106, 0.2689954936504364, 0.1881893426179886, 0.2150678187608719, 0.14432872831821442, 0.20273351669311523, 0.1951741725206375, 0.20388269424438477, 0.26212528347969055, 0.16737906634807587, 0.1870533674955368, 0.21891845762729645, 0.17954464256763458, 0.22458961606025696, 0.22820980846881866, 0.2019929438829422, 0.20505356788635254, 0.21609307825565338, 0.2701319754123688, 0.09731172025203705, 0.19714023172855377, 0.20096972584724426, 0.23392345011234283, 0.19289390742778778, 0.1724219024181366, 0.2052789032459259, 0.2846332788467407, 0.14489731192588806, 0.24492107331752777, 0.2236025631427765, 0.1755642145872116, 0.11367949098348618, 0.19966740906238556, 0.21321800351142883, 0.17508220672607422, 0.201216921210289, 0.25446876883506775, 0.19019381701946259, 0.13065272569656372, 0.2449333518743515, 0.1378016620874405, 0.21040843427181244, 0.13323596119880676, 0.15822555124759674, 0.13157708942890167, 0.14940515160560608, 0.22203654050827026, 0.20262748003005981, 0.15817080438137054, 0.19231009483337402, 0.21434159576892853, 0.11402707546949387, 0.25697243213653564, 0.17791682481765747, 0.21512529253959656, 0.16699165105819702, 0.28764697909355164, 0.21798188984394073, 0.16208942234516144, 0.23274850845336914, 0.1427130103111267, 0.2412038892507553, 0.24182814359664917, 0.22463029623031616, 0.24034060537815094, 0.19250376522541046, 0.20944713056087494, 0.2327384203672409, 0.15189573168754578, 0.18043212592601776, 0.18306370079517365, 0.1569395512342453, 0.2127869576215744, 0.16851472854614258, 0.13510417938232422, 0.1735372096300125, 0.15740230679512024, 0.207279771566391, 0.1582246869802475, 0.14690905809402466, 0.22713623940944672, 0.1645428091287613, 0.13631142675876617, 0.18151536583900452, 0.18849250674247742, 0.2117973119020462, 0.20686574280261993, 0.18146884441375732, 0.1974475085735321, 0.21014106273651123, 0.2189040184020996, 0.22559496760368347, 0.12053588777780533, 0.21017077565193176, 0.21397878229618073, 0.2238132357597351, 0.1479174792766571, 0.10959084331989288, 0.20624621212482452, 0.17638713121414185, 0.12388810515403748, 0.17078426480293274, 0.16800332069396973, 0.19992366433143616, 0.1949639916419983, 0.1898486316204071, 0.22924020886421204, 0.16846011579036713, 0.17503400146961212, 0.1994159072637558, 0.1490650326013565, 0.21729376912117004, 0.13472408056259155, 0.22905535995960236, 0.16246157884597778, 0.16818790137767792, 0.22173991799354553, 0.22778677940368652, 0.2601153254508972, 0.18363109230995178, 0.17685726284980774, 0.22491545975208282, 0.17133748531341553, 0.1853165626525879, 0.21294492483139038, 0.20579864084720612, 0.21800395846366882, 0.199254110455513, 0.16994057595729828, 0.22016723453998566, 0.24496136605739594, 0.17235055565834045, 0.1512288749217987, 0.1616113781929016, 0.17300257086753845, 0.1951020061969757, 0.12203649431467056, 0.1856447011232376, 0.21441997587680817, 0.15850001573562622, 0.22145050764083862, 0.16148295998573303, 0.1371910125017166, 0.18115031719207764, 0.16617900133132935, 0.17771083116531372, 0.20400285720825195, 0.2451225072145462, 0.23515568673610687, 0.17040187120437622, 0.14986534416675568, 0.21100780367851257, 0.1205599382519722, 0.18517902493476868, 0.1529981642961502, 0.20607376098632812, 0.19220863282680511, 0.15830908715724945, 0.20363017916679382, 0.18901784718036652, 0.20674781501293182, 0.181990846991539, 0.2150811403989792, 0.26277223229408264, 0.14455996453762054, 0.2376500517129898, 0.22906112670898438, 0.1495763212442398, 0.1656005084514618, 0.06525006890296936, 0.20895794034004211, 0.18297824263572693, 0.18359968066215515, 0.16068869829177856, 0.26246538758277893, 0.1098950058221817, 0.20511868596076965, 0.20137368142604828, 0.17366357147693634, 0.13676251471042633, 0.19067814946174622, 0.1195591539144516, 0.21821409463882446, 0.1725381761789322, 0.16291068494319916, 0.19219334423542023, 0.21345782279968262, 0.2023826390504837, 0.18530261516571045, 0.27165618538856506, 0.16397762298583984, 0.18894687294960022, 0.2102210968732834, 0.18721213936805725, 0.22331476211547852, 0.19311797618865967, 0.12669774889945984, 0.1461712121963501, 0.1902855634689331, 0.18489748239517212, 0.22852542996406555, 0.198202446103096, 0.19045795500278473, 0.16738295555114746, 0.2048187553882599, 0.19844916462898254, 0.20340299606323242, 0.23638828098773956, 0.20783522725105286, 0.19764824211597443, 0.2583949565887451, 0.21661806106567383, 0.20628778636455536, 0.15437659621238708, 0.20516617596149445, 0.25352743268013, 0.16302789747714996, 0.19347484409809113, 0.1294083148241043, 0.16955247521400452, 0.23934738337993622, 0.20406726002693176, 1.2318475246429443, 2.1029837131500244, 1.8466973304748535, 1.608482003211975, 2.4679336547851562, 1.368752360343933, 2.3452956676483154, 1.6320196390151978, 1.3239144086837769, 2.090038537979126, 2.7806942462921143, 1.5927616357803345, 2.2058005332946777, 2.6726653575897217, 1.4859169721603394, 1.7567733526229858, 1.4134817123413086, 1.5509754419326782, 1.4191334247589111, 1.862363338470459, 1.8618704080581665, 1.6498284339904785, 2.2144320011138916, 1.2714667320251465, 1.8415424823760986, 2.0519769191741943, 2.098515510559082, 1.3413728475570679, 2.1652541160583496, 1.6329580545425415, 2.0148518085479736, 1.7086803913116455, 1.383039116859436, 1.9792474508285522, 1.7776033878326416, 1.5844274759292603, 2.729112386703491, 1.3225042819976807, 2.447709321975708, 2.2263565063476562, 2.6952240467071533, 2.1950430870056152, 1.4300085306167603, 1.7457304000854492, 3.0362465381622314, 1.6157193183898926, 1.4157785177230835, 1.9744873046875, 1.6102203130722046, 2.2265119552612305, 1.1569204330444336, 1.5232146978378296, 1.731484055519104, 2.283810615539551, 1.3410156965255737, 1.4096355438232422, 2.3076281547546387, 1.8800251483917236, 1.900134801864624, 2.0675506591796875, 1.9705842733383179, 1.9193458557128906, 1.848824381828308, 1.8117039203643799, 1.672914743423462, 1.8149595260620117, 1.261404037475586, 1.7653255462646484, 1.7190475463867188, 2.135361671447754, 1.7190706729888916, 1.8499350547790527, 1.8393518924713135, 1.5024874210357666, 1.7617814540863037, 1.6589748859405518, 2.4660162925720215, 1.221742868423462, 2.0935420989990234, 2.888343095779419, 1.1400903463363647, 1.438921570777893, 1.324861764907837, 2.035855293273926, 1.3719761371612549, 2.1110968589782715, 1.6320985555648804, 2.1175475120544434, 1.6987829208374023, 2.0770363807678223, 1.3348731994628906, 1.8606503009796143, 0.896278977394104, 1.6466034650802612, 1.9878534078598022, 1.9816079139709473, 2.5381081104278564, 2.254603385925293, 2.1348533630371094, 1.7875616550445557, 1.8474829196929932, 1.9573249816894531, 2.1454355716705322, 1.2814788818359375, 2.1456878185272217, 2.1634764671325684, 2.3508622646331787, 1.507271647453308, 1.3962554931640625, 2.4827499389648438, 1.4903723001480103, 1.2075892686843872, 2.008585214614868, 2.6966049671173096, 2.0248970985412598, 2.867973804473877, 2.5163233280181885, 1.8240036964416504, 1.8036657571792603, 1.7338008880615234, 1.5289897918701172, 1.4521217346191406, 1.9009233713150024, 2.105088710784912, 2.2818918228149414, 2.4908387660980225, 1.7347391843795776, 2.321319341659546, 1.1706761121749878, 1.8809318542480469, 2.1634581089019775, 2.2734310626983643, 1.797252893447876, 2.3536758422851562, 2.0635428428649902, 2.5993340015411377, 2.521120309829712, 1.3493969440460205, 1.6023151874542236, 2.4289491176605225, 1.927950143814087, 2.450575590133667, 2.4422426223754883, 1.5231847763061523, 1.5183112621307373, 1.4401599168777466, 1.5242801904678345, 1.5540716648101807, 1.3326348066329956, 1.7475248575210571, 1.6692609786987305, 2.6586461067199707, 2.420301675796509, 2.168613910675049, 2.0362606048583984, 2.043475866317749, 1.4886950254440308, 2.4273276329040527, 1.8457984924316406, 1.34808349609375, 2.081019401550293, 1.6476398706436157, 1.9257383346557617, 1.4219970703125, 1.2545361518859863, 2.0673487186431885, 1.657065987586975, 1.8261797428131104, 2.1938364505767822, 1.660870909690857, 2.244694232940674, 1.2597442865371704, 1.3737305402755737, 1.8764545917510986, 1.3747215270996094, 2.367861270904541, 1.7366371154785156, 1.4220880270004272, 1.9621435403823853, 2.6312882900238037, 1.7363008260726929, 1.2619669437408447, 1.436145544052124, 2.1811864376068115, 1.5082610845565796, 1.9297012090682983, 1.6075350046157837, 1.921873688697815, 1.4043464660644531, 2.0452029705047607, 2.3078553676605225, 1.355006217956543, 1.8512279987335205, 1.5777661800384521, 1.312280297279358, 2.2629027366638184, 1.1529333591461182, 1.0007590055465698, 2.2038307189941406, 2.5588178634643555, 2.06589937210083, 1.204622507095337, 1.4446163177490234, 1.122604250907898, 2.448002338409424, 1.0202243328094482, 1.9385223388671875, 1.720003366470337, 2.1099367141723633, 1.476191520690918, 1.4319206476211548, 1.1733884811401367, 2.630375862121582, 1.2234995365142822, 3.057685136795044, 1.2259581089019775, 1.4879463911056519, 1.269277811050415, 2.355024576187134, 1.1643180847167969, 1.3184356689453125, 1.6690679788589478, 1.4907479286193848, 1.2812381982803345, 2.451403856277466, 1.9397982358932495, 1.4117672443389893, 1.53895902633667, 1.6041704416275024, 1.0662906169891357, 1.179075002670288, 2.0285797119140625, 2.6440680027008057, 1.211385726928711, 2.6721763610839844, 1.487099528312683, 2.108485221862793, 1.8367241621017456, 1.0944570302963257, 2.1359431743621826, 2.08626127243042, 1.9835551977157593, 2.263580799102783, 1.643540859222412, 1.9341638088226318, 2.3811287879943848, 1.617144227027893, 1.40376615524292, 2.312389373779297, 1.902524709701538, 1.4336473941802979, 1.2793684005737305, 2.031092882156372, 1.3527309894561768, 1.6289194822311401, 2.0288636684417725, 1.4056992530822754, 2.4348340034484863, 1.1166589260101318, 2.0079989433288574, 2.108921527862549, 1.7562992572784424, 1.7092232704162598, 1.8071588277816772, 1.142293930053711, 1.5622450113296509, 2.1477370262145996, 2.1400656700134277, 1.6230509281158447, 2.06797456741333, 2.1042733192443848, 1.8550617694854736, 1.5445932149887085, 1.478367567062378, 2.1463747024536133, 1.723740816116333, 1.5778061151504517, 1.6421329975128174, 2.465646266937256, 2.4031386375427246, 1.4777618646621704, 2.3511619567871094, 2.308302879333496, 1.9499778747558594, 1.9006845951080322, 1.3766998052597046, 1.9401136636734009, 1.4241966009140015, 1.9957917928695679, 1.9752142429351807, 1.589258074760437, 1.9626165628433228, 1.9429030418395996, 1.8627653121948242, 1.760825276374817, 2.347662925720215, 2.427532196044922, 2.663694381713867, 1.6246449947357178, 1.7166225910186768, 42.31633758544922, 58.73086929321289, 208.50811767578125, 42.2140998840332, 104.01898193359375, 132.57574462890625, 59.006473541259766, 23.19903564453125, 41.848201751708984, 59.70974349975586, 66.777099609375, 175.82962036132812, 280.5229797363281, 81.47222137451172, 134.75022888183594, 104.01019287109375, 83.39279174804688, 79.46402740478516, 63.094364166259766, 102.66790771484375, 128.27862548828125, 87.5889663696289, 49.93661880493164, 202.1593780517578, 190.57522583007812, 222.98782348632812, 200.98753356933594, 35.5615234375, 108.501708984375, 99.62007904052734, 165.02288818359375, 145.44921875, 42.21319580078125, 290.10455322265625, 111.71294403076172, 422.611328125, 150.53643798828125, 64.14727020263672, 56.716522216796875, 250.0830078125, 141.46575927734375, 135.77638244628906, 152.966552734375, 204.7272491455078, 79.12680053710938, 57.065731048583984, 31.09439468383789, 213.9071044921875, 37.09307861328125, 48.34954071044922, 245.3485870361328, 192.4222412109375, 78.43343353271484, 125.10092163085938, 166.37261962890625, 474.4588928222656, 118.86956787109375, 286.0023193359375, 92.3160171508789, 68.3541488647461, 182.72679138183594, 304.543701171875, 68.11845397949219, 52.35757064819336, 214.4224395751953, 95.80431365966797, 45.34962463378906, 160.30908203125, 165.73033142089844, 33.28034210205078, 123.45755767822266, 44.13770294189453, 269.5243225097656, 163.1268310546875, 236.7377471923828, 100.93436431884766, 241.851806640625, 62.5054931640625, 74.46292114257812, 50.4117431640625, 127.13491821289062, 82.86326599121094, 98.23931121826172, 126.34593200683594, 120.22724151611328, 28.87408447265625, 34.79670333862305, 305.6361389160156, 86.0906982421875, 124.97113037109375, 65.34515380859375, 59.35613250732422, 196.39756774902344, 93.82508850097656, 31.112192153930664, 160.84088134765625, 37.18259811401367, 37.7005615234375, 195.88780212402344, 58.75711441040039, 109.85743713378906, 84.46733856201172, 50.2999267578125, 56.47595977783203, 134.0625762939453, 250.40350341796875, 321.6641845703125, 83.26507568359375, 100.00922393798828, 110.82384490966797, 107.81499481201172, 96.40845489501953, 100.49603271484375, 202.2880096435547, 119.4747543334961, 72.35655212402344, 87.9069595336914, 117.00146484375, 160.095703125, 123.82142639160156, 36.82501220703125, 144.94268798828125, 271.99652099609375, 417.2899475097656, 105.92948150634766, 64.92156982421875, 174.86572265625, 177.3519287109375, 93.80718231201172, 67.41650390625, 148.74929809570312, 86.579345703125, 127.822021484375, 53.13134765625, 97.29259490966797, 77.10470581054688, 77.0262451171875, 247.92581176757812, 382.656005859375, 312.83636474609375, 208.3662109375, 232.2030792236328, 46.9799690246582, 92.21318817138672, 198.227294921875, 64.95825958251953, 170.74887084960938, 97.70947265625, 99.259765625, 53.532470703125, 81.8782958984375, 51.32082748413086, 221.0152130126953, 113.82691192626953, 74.3748779296875, 43.68597412109375, 256.4936218261719, 56.72430419921875, 36.610313415527344, 81.06097412109375, 68.0032958984375, 45.6859130859375, 259.3463134765625, 193.00942993164062, 161.91531372070312, 105.0205078125, 132.74940490722656, 177.5625762939453, 137.07406616210938, 94.7337646484375, 109.140869140625, 445.267333984375, 123.73993682861328, 40.94863510131836, 93.77708435058594, 138.64486694335938, 43.654052734375, 37.36431884765625, 49.38113021850586, 131.08132934570312, 42.742919921875, 78.06404876708984, 85.21688079833984, 226.3526153564453, 142.79595947265625, 110.34819793701172, 136.72967529296875, 287.5907287597656, 112.12567138671875, 367.36627197265625, 92.1823501586914, 132.09886169433594, 144.21746826171875, 79.82551574707031, 158.58251953125, 69.10037231445312, 44.608154296875, 85.79995727539062, 167.9095458984375, 132.66168212890625, 131.62939453125, 307.95135498046875, 119.12120819091797, 62.939208984375, 154.17251586914062, 114.86719512939453, 137.7013397216797, 54.1805419921875, 120.12866973876953, 204.4824981689453, 174.83206176757812, 394.2332458496094, 70.28545379638672, 42.5140380859375, 106.96597290039062, 183.77503967285156, 101.14847564697266, 92.10731506347656, 275.25054931640625, 42.79897689819336, 86.6156005859375, 210.7187042236328, 193.8099822998047, 57.50843811035156, 201.5126953125, 34.6010856628418, 178.80322265625, 87.88968658447266, 169.2117919921875, 195.6359405517578, 51.21697998046875, 188.9375, 163.124755859375, 115.326416015625, 38.0032958984375, 121.42684936523438, 97.88184356689453, 196.8407440185547, 147.3741912841797, 120.54230499267578, 121.49365997314453, 39.98431396484375, 196.22412109375, 169.013671875, 67.1083984375, 51.94009017944336, 67.82754516601562, 65.24089050292969, 319.0577392578125, 122.29949951171875, 41.11518478393555, 114.78924560546875, 189.04638671875, 74.8104248046875, 77.97744750976562, 111.1659164428711, 116.197509765625, 81.397216796875, 144.85780334472656, 224.5628204345703, 159.46278381347656, 60.53921127319336, 241.411865234375, 98.6826171875, 107.58565521240234, 93.11144256591797, 148.56793212890625, 119.9617919921875, 213.2429656982422, 38.578025817871094, 191.9851837158203, 58.57637405395508, 138.93655395507812, 257.93328857421875, 289.3144836425781, 237.22100830078125, 216.6172637939453, 122.24928283691406, 387.09002685546875, 146.50184631347656, 137.4029083251953, 88.64836120605469, 65.73271179199219, 125.04786682128906, 152.22645568847656, 73.35932922363281, 184.50784301757812, 78.87409210205078, 70.93325805664062, 187.4582061767578, 46.12968826293945, 193.24273681640625, 33.1885986328125, 74.19341278076172, 95.72314453125, 267.7475280761719, 55.11732482910156, 133.89808654785156, 159.3792266845703, 75.9798812866211, 2.0152273178100586, 3.2859485149383545, 1.9936803579330444, 3.055652379989624, 2.3228633403778076, 3.3049707412719727, 1.7144560813903809, 3.195385456085205, 3.5124404430389404, 2.4431426525115967, 2.698538064956665, 2.298633337020874, 2.797985076904297, 1.5864418745040894, 2.0004708766937256, 2.651402473449707, 4.1495890617370605, 2.1014251708984375, 3.3826513290405273, 3.2529172897338867, 1.3598791360855103, 2.0738844871520996, 1.9050599336624146, 3.335942268371582, 2.7992565631866455, 3.2760305404663086, 2.8739635944366455, 3.3731799125671387, 1.7189911603927612, 1.4956451654434204, 3.7922301292419434, 2.1030588150024414, 3.683659553527832, 2.0087413787841797, 2.5045814514160156, 2.8511722087860107, 1.5416216850280762, 2.5460877418518066, 2.40399169921875, 2.9062530994415283, 3.185106039047241, 2.868701219558716, 2.18790340423584, 2.4177944660186768, 2.755540609359741, 2.2525527477264404, 3.411182165145874, 2.9394590854644775, 1.2922391891479492, 1.8118523359298706, 2.1463124752044678, 1.8881868124008179, 1.353048324584961, 2.001225471496582, 2.9734511375427246, 2.043696403503418, 3.017707109451294, 2.0569851398468018, 1.6278448104858398, 2.3134920597076416, 1.6458481550216675, 2.9218740463256836, 2.9751408100128174, 2.4871461391448975, 2.009871006011963, 2.3377678394317627, 2.010594367980957, 2.108699083328247, 2.834028959274292, 3.0103728771209717, 2.4239754676818848, 3.0633208751678467, 1.659900426864624, 2.12538480758667, 3.046520233154297, 3.129596710205078, 3.4454405307769775, 2.6787285804748535, 2.6477153301239014, 3.275151252746582, 2.847654342651367, 2.488417387008667, 1.8743419647216797, 3.044633150100708, 2.8904850482940674, 3.1628024578094482, 1.4018774032592773, 1.9724918603897095, 4.239965915679932, 2.521984100341797, 2.2092885971069336, 3.1017048358917236, 2.7292425632476807, 3.2030622959136963, 2.8089935779571533, 2.141219139099121, 1.578486442565918, 2.640974760055542, 2.175753593444824, 1.5187640190124512, 3.051906108856201, 2.4804582595825195, 3.339864492416382, 3.0056183338165283, 1.639748454093933, 3.52734112739563, 2.352048397064209, 2.3073909282684326, 2.952216148376465, 2.104539155960083, 2.841080904006958, 2.1340813636779785, 2.0345194339752197, 2.048079252243042, 3.0488269329071045, 3.354238510131836, 3.05159854888916, 2.6777679920196533, 2.2958526611328125, 1.4513393640518188, 2.4161980152130127, 1.6483588218688965, 1.6850171089172363, 3.0913116931915283, 2.245805263519287, 2.7608745098114014, 1.8547430038452148, 1.8903194665908813, 1.582239031791687, 2.1912546157836914, 2.4543533325195312, 2.164597511291504, 2.921189546585083, 1.994862675666809, 1.9566097259521484, 2.3039004802703857, 2.7728261947631836, 1.708012342453003, 3.9101719856262207, 2.7776145935058594, 3.4929943084716797, 3.128323793411255, 2.6238067150115967, 2.7121477127075195, 3.8542604446411133, 2.1659889221191406, 2.6036431789398193, 2.1029775142669678, 2.1426544189453125, 1.3411915302276611, 3.5388476848602295, 1.866347312927246, 2.1351022720336914, 2.830298662185669, 1.4136403799057007, 2.9249894618988037, 2.599318504333496, 2.92547345161438, 2.530961751937866, 3.404637575149536, 2.1365692615509033, 2.2681455612182617, 2.1246118545532227, 2.1233317852020264, 2.0367305278778076, 2.111630439758301, 2.0746567249298096, 2.827343463897705, 1.9248915910720825, 2.141993284225464, 2.257800340652466, 1.3799734115600586, 3.1173555850982666, 1.4192899465560913, 2.020328998565674, 3.969383955001831, 1.8762942552566528, 3.42990779876709, 2.5271310806274414, 1.538598656654358, 2.305466651916504, 2.554631233215332, 1.699485182762146, 2.9726550579071045, 2.0562422275543213, 1.0376735925674438, 3.7420201301574707, 2.143829107284546, 3.5327024459838867, 2.5025758743286133, 2.2456283569335938, 2.8968944549560547, 1.9649343490600586, 3.1668498516082764, 1.572245717048645, 2.9089202880859375, 2.5189647674560547, 2.8836605548858643, 3.532212972640991, 2.2125093936920166, 1.849146842956543, 4.1025519371032715, 1.6534461975097656, 3.016138792037964, 2.297287940979004, 3.5952775478363037, 2.322464942932129, 3.0386135578155518, 2.4291625022888184, 2.425726890563965, 1.6828545331954956, 2.5742993354797363, 1.615071415901184, 3.590620756149292, 2.053117275238037, 2.6786530017852783, 4.141360759735107, 1.517399549484253, 2.3318686485290527, 2.4756674766540527, 2.963677406311035, 2.579437255859375, 2.6671271324157715, 2.6864993572235107, 3.117669105529785, 2.461195945739746, 2.5650360584259033, 1.7974908351898193, 2.77652645111084, 2.6826870441436768, 2.7660186290740967, 3.2722740173339844, 1.7670069932937622, 2.929272413253784, 2.4868686199188232, 1.6037168502807617, 1.935202956199646, 2.8201897144317627, 2.7854068279266357, 3.1775894165039062, 2.5471174716949463, 3.4383325576782227, 2.247260093688965, 3.237738847732544, 3.37628173828125, 2.88265323638916, 2.5587217807769775, 1.769251823425293, 1.7623416185379028, 2.8917076587677, 2.963253974914551, 2.8901050090789795, 1.9934606552124023, 3.1517040729522705, 1.3893537521362305, 2.7540950775146484, 1.981302261352539, 3.5398049354553223, 3.086663246154785, 3.0118236541748047, 3.148979663848877, 1.559228539466858, 3.4277431964874268, 2.5513410568237305, 1.3023922443389893, 2.9201066493988037, 2.857736825942993, 3.0759477615356445, 1.818021535873413, 2.454556465148926, 1.9826782941818237, 2.586181879043579, 2.938676118850708, 3.9649572372436523, 2.0817575454711914, 2.5259222984313965, 1.949480652809143, 2.336329936981201, 1.9986989498138428, 1.8818895816802979, 2.7493133544921875, 1.625481367111206, 2.150430917739868, 2.7078757286071777, 1.6046743392944336, 1.853475570678711, 2.7471160888671875, 3.2137913703918457, 2.9646031856536865, 3.4359819889068604, 3.5319740772247314, 2.5141918659210205, 3.1101012229919434, 1.971217155456543, 1.8847848176956177, 3.1232120990753174, 2.475175142288208, 2.972634792327881, 2.5523996353149414, 3.765265703201294, 0.22730563580989838, 0.1263076364994049, 0.19264639914035797, 0.15025144815444946, 0.15618868172168732, 0.1696140617132187, 0.21206752955913544, 0.1637934148311615, 0.1943376362323761, 0.21373355388641357, 0.24609358608722687, 0.16143158078193665, 0.23486876487731934, 0.21563979983329773, 0.1822655200958252, 0.19756470620632172, 0.20136256515979767, 0.2126874476671219, 0.1927167922258377, 0.18637330830097198, 0.14645221829414368, 0.20880545675754547, 0.1805858314037323, 0.16715602576732635, 0.2591133415699005, 0.2006942629814148, 0.292621910572052, 0.1899588704109192, 0.16454879939556122, 0.22014114260673523, 0.15513736009597778, 0.18845322728157043, 0.23451025784015656, 0.23672664165496826, 0.1193167194724083, 0.2520448565483093, 0.21463850140571594, 0.23644402623176575, 0.15200760960578918, 0.15866805613040924, 0.1582755297422409, 0.17755275964736938, 0.17737650871276855, 0.16471447050571442, 0.22464711964130402, 0.11796873062849045, 0.10436427593231201, 0.20521776378154755, 0.20162418484687805, 0.23857982456684113, 0.2149520218372345, 0.1473410725593567, 0.18501663208007812, 0.23244895040988922, 0.16717660427093506, 0.2663489580154419, 0.2603376507759094, 0.18447387218475342, 0.19073635339736938, 0.20979617536067963, 0.25616899132728577, 0.15646573901176453, 0.2202574610710144, 0.170790895819664, 0.14697347581386566, 0.25467193126678467, 0.19434669613838196, 0.21647235751152039, 0.16552074253559113, 0.2288466989994049, 0.13692252337932587, 0.18166886270046234, 0.18054059147834778, 0.21381425857543945, 0.25309672951698303, 0.17677153646945953, 0.13298392295837402, 0.13798533380031586, 0.22631362080574036, 0.19935107231140137, 0.16892282664775848, 0.1942884922027588, 0.15210361778736115, 0.14831900596618652, 0.22917777299880981, 0.15300250053405762, 0.2020782232284546, 0.25950002670288086, 0.15672652423381805, 0.14604730904102325, 0.14919105172157288, 0.16054579615592957, 0.20930646359920502, 0.20715618133544922, 0.21976256370544434, 0.15382277965545654, 0.17874440550804138, 0.24372035264968872, 0.23267824947834015, 0.16962207853794098, 0.21754762530326843, 0.16360031068325043, 0.19098147749900818, 0.28516578674316406, 0.22798976302146912, 0.2315887063741684, 0.16726131737232208, 0.20692171156406403, 0.16856646537780762, 0.19447267055511475, 0.2366948127746582, 0.21447589993476868, 0.14192838966846466, 0.20678512752056122, 0.2657356560230255, 0.18492119014263153, 0.21532157063484192, 0.1646495908498764, 0.23652900755405426, 0.1803950071334839, 0.12357135862112045, 0.23543331027030945, 0.24090568721294403, 0.23045030236244202, 0.22127015888690948, 0.1963348686695099, 0.1771298199892044, 0.20783209800720215, 0.21645519137382507, 0.20238035917282104, 0.1640183925628662, 0.16213522851467133, 0.18155528604984283, 0.22905439138412476, 0.22737962007522583, 0.176615372300148, 0.19432778656482697, 0.19986964762210846, 0.21107089519500732, 0.18726272881031036, 0.1583050936460495, 0.18977594375610352, 0.20849445462226868, 0.18403272330760956, 0.15881744027137756, 0.1277633011341095, 0.19164347648620605, 0.18192961812019348, 0.21446844935417175, 0.19886727631092072, 0.1556803584098816, 0.17845427989959717, 0.14037498831748962, 0.16670764982700348, 0.17746761441230774, 0.2083207219839096, 0.1472192108631134, 0.20082953572273254, 0.19483119249343872, 0.15476930141448975, 0.19370611011981964, 0.18577732145786285, 0.1810833364725113, 0.22677934169769287, 0.20666438341140747, 0.17944104969501495, 0.24337470531463623, 0.21589237451553345, 0.16665254533290863, 0.19805820286273956, 0.1558874249458313, 0.2009425312280655, 0.14528301358222961, 0.16928735375404358, 0.19186536967754364, 0.2618139684200287, 0.16758354008197784, 0.19733145833015442, 0.16440604627132416, 0.20681865513324738, 0.23400923609733582, 0.2322710007429123, 0.23259525001049042, 0.1833910346031189, 0.17897935211658478, 0.24799026548862457, 0.16792774200439453, 0.13965342938899994, 0.20726150274276733, 0.21275094151496887, 0.20185163617134094, 0.1932661086320877, 0.20791952311992645, 0.2267674207687378, 0.18619680404663086, 0.14048494398593903, 0.26736053824424744, 0.19901643693447113, 0.1855989396572113, 0.20377697050571442, 0.22061827778816223, 0.28653964400291443, 0.21851825714111328, 0.27791279554367065, 0.160008504986763, 0.2195461541414261, 0.1428564041852951, 0.2510446310043335, 0.2453867644071579, 0.21919086575508118, 0.16481149196624756, 0.1871553510427475, 0.21534007787704468, 0.1253911405801773, 0.18906143307685852, 0.23409457504749298, 0.1918785125017166, 0.2606193423271179, 0.21989238262176514, 0.24901488423347473, 0.17568635940551758, 0.20681968331336975, 0.18082495033740997, 0.23588193953037262, 0.18173936009407043, 0.1693735420703888, 0.22462987899780273, 0.22364147007465363, 0.16509023308753967, 0.23646126687526703, 0.22434087097644806, 0.22544199228286743, 0.20470252633094788, 0.17070968449115753, 0.2298613339662552, 0.24424883723258972, 0.20949013531208038, 0.2122349888086319, 0.20176909863948822, 0.11260157078504562, 0.2161991447210312, 0.2652958929538727, 0.17182548344135284, 0.2101791352033615, 0.2064410299062729, 0.21729260683059692, 0.2622753977775574, 0.280983567237854, 0.19283492863178253, 0.2068355828523636, 0.2022135853767395, 0.23348365724086761, 0.19880452752113342, 0.13769622147083282, 0.21459689736366272, 0.16512790322303772, 0.2250114232301712, 0.2064519226551056, 0.26432308554649353, 0.18811602890491486, 0.19596725702285767, 0.20294292271137238, 0.1975823938846588, 0.1766788810491562, 0.21503539383411407, 0.24381780624389648, 0.2163706123828888, 0.1893751472234726, 0.22549574077129364, 0.29752635955810547, 0.1737143099308014, 0.18826062977313995, 0.21672938764095306, 0.2033921778202057, 0.23186282813549042, 0.26521074771881104, 0.1891361027956009, 0.275210440158844, 0.18118701875209808, 0.18639212846755981, 0.13745616376399994, 0.1828741580247879, 0.19152049720287323, 0.1799144446849823, 0.2642362415790558, 0.2629162073135376, 0.13256007432937622, 0.1784999817609787, 0.20823806524276733, 0.1829942911863327, 0.16563543677330017, 0.1398887038230896, 0.19783137738704681, 0.20009180903434753, 0.2099846601486206, 0.2048931121826172, 0.12814418971538544, 0.2288801074028015, 0.21624663472175598, 0.1962631195783615, 1.8102736473083496, 0.921708881855011, 1.6930423974990845, 1.8066812753677368, 2.4391467571258545, 1.4602587223052979, 1.7153875827789307, 1.6885656118392944, 2.287673234939575, 2.20786452293396, 1.031038761138916, 1.9998834133148193, 1.9619944095611572, 1.2704088687896729, 1.3109420537948608, 3.5898220539093018, 2.3541901111602783, 1.8757575750350952, 1.873569130897522, 1.1792378425598145, 2.215826988220215, 1.883548378944397, 1.5000425577163696, 1.796051025390625, 0.9592079520225525, 1.6320452690124512, 1.6487585306167603, 1.6987236738204956, 1.4476995468139648, 3.175605058670044, 1.7925710678100586, 1.6918413639068604, 2.114659309387207, 2.1275620460510254, 3.1926486492156982, 1.6638017892837524, 1.742738962173462, 1.2332789897918701, 1.659798502922058, 1.8633571863174438, 3.0956223011016846, 2.0014336109161377, 2.052158832550049, 1.7368148565292358, 2.6682164669036865, 1.0147944688796997, 2.5549163818359375, 2.0733249187469482, 2.1456034183502197, 2.088071823120117, 2.611877679824829, 1.014732837677002, 1.3242541551589966, 1.7964458465576172, 1.9131563901901245, 1.9463045597076416, 1.394525170326233, 1.2698650360107422, 1.5251312255859375, 1.828308343887329, 1.9189904928207397, 1.6355504989624023, 1.4203014373779297, 1.5803098678588867, 1.6788249015808105, 1.103877305984497, 1.49260675907135, 2.367722988128662, 1.590193748474121, 1.5179601907730103, 2.463069200515747, 2.267207145690918, 1.730233073234558, 1.8485788106918335, 2.54264497756958, 2.110149383544922, 1.8139158487319946, 1.3095699548721313, 1.2925329208374023, 2.135941982269287, 1.607774019241333, 2.733212947845459, 1.933108925819397, 2.4189157485961914, 3.4351017475128174, 1.5719718933105469, 1.613411784172058, 1.7307430505752563, 1.342450737953186, 1.990468978881836, 1.7293621301651, 0.9307693839073181, 1.3619552850723267, 2.252887725830078, 2.4206955432891846, 2.214892864227295, 1.682236909866333, 2.6302402019500732, 2.1577723026275635, 1.1373642683029175, 1.5529273748397827, 2.1843316555023193, 1.524035096168518, 3.740049123764038, 2.537156105041504, 2.0093648433685303, 2.5321712493896484, 1.8141552209854126, 2.4658572673797607, 1.7138214111328125, 3.0446441173553467, 2.3125526905059814, 2.469747543334961, 1.2844501733779907, 1.5649439096450806, 1.2733206748962402, 2.3767685890197754, 2.0726165771484375, 1.8756927251815796, 1.8045717477798462, 1.989620566368103, 1.84185791015625, 1.6353286504745483, 1.484256386756897, 1.16318678855896, 1.3839304447174072, 1.5760369300842285, 1.94290030002594, 3.213107109069824, 1.2819305658340454, 1.879041075706482, 2.4524247646331787, 2.0917768478393555, 2.2976062297821045, 3.575167655944824, 2.3716981410980225, 2.326014995574951, 2.326143980026245, 1.8675428628921509, 2.079655647277832, 0.8917913436889648, 2.6528027057647705, 1.6973168849945068, 2.3331778049468994, 1.7326627969741821, 2.827360153198242, 2.1427299976348877, 1.9184582233428955, 2.1332626342773438, 1.8202669620513916, 1.8667608499526978, 2.0517547130584717, 1.4790444374084473, 1.875222086906433, 2.719085216522217, 1.7403472661972046, 1.2982282638549805, 1.866003394126892, 1.9786218404769897, 1.5170114040374756, 1.284248948097229, 2.000251531600952, 1.8816356658935547, 2.5494225025177, 1.7417287826538086, 2.108609914779663, 2.5742592811584473, 1.3827149868011475, 2.0628583431243896, 1.7183866500854492, 2.2770767211914062, 1.4283376932144165, 1.4646142721176147, 2.0886337757110596, 1.9282352924346924, 1.3087173700332642, 1.9401558637619019, 2.462893486022949, 1.9110732078552246, 2.3376522064208984, 2.708014726638794, 1.923082947731018, 1.8383049964904785, 1.9632930755615234, 2.2607076168060303, 1.669546127319336, 1.302886724472046, 2.018380880355835, 2.0836706161499023, 1.7984994649887085, 2.248110294342041, 1.5688896179199219, 1.7106119394302368, 1.6762510538101196, 2.0549542903900146, 1.3502752780914307, 1.8652279376983643, 1.7477518320083618, 1.8709291219711304, 1.4107229709625244, 2.2911651134490967, 2.1528618335723877, 1.7824795246124268, 2.620551109313965, 1.8160353899002075, 1.6028194427490234, 1.4968152046203613, 1.7311804294586182, 1.266082763671875, 2.190974473953247, 1.6559233665466309, 1.8072808980941772, 1.6150474548339844, 2.2548158168792725, 1.554329514503479, 1.5789873600006104, 2.428536891937256, 2.346334457397461, 1.2859405279159546, 1.947771668434143, 2.28481388092041, 1.7155557870864868, 1.8990892171859741, 2.8705646991729736, 1.9343492984771729, 1.6246721744537354, 1.4036962985992432, 1.4741848707199097, 1.7790082693099976, 1.915366768836975, 1.287534475326538, 1.8555715084075928, 1.9168264865875244, 2.8253440856933594, 1.9420992136001587, 2.048234462738037, 1.7463316917419434, 1.9283758401870728, 2.477900981903076, 1.640918493270874, 1.4298958778381348, 2.0897316932678223, 3.1037750244140625, 2.2812349796295166, 1.4620361328125, 2.035604476928711, 2.2855870723724365, 1.9082764387130737, 2.794315814971924, 1.9707088470458984, 2.965911865234375, 1.4965908527374268, 2.3331727981567383, 2.0710487365722656, 2.03739595413208, 2.5159687995910645, 2.1337387561798096, 1.5108903646469116, 2.352047920227051, 2.332359552383423, 1.9567043781280518, 1.4565691947937012, 2.4220895767211914, 2.2060766220092773, 2.0962109565734863, 2.1097164154052734, 2.719923973083496, 1.614890694618225, 1.4497416019439697, 1.3528788089752197, 1.5696499347686768, 2.0709266662597656, 1.9280951023101807, 2.8848443031311035, 1.6239501237869263, 2.7328860759735107, 1.8439888954162598, 1.951427698135376, 2.86163330078125, 1.501240611076355, 2.100464344024658, 1.8103523254394531, 1.5684603452682495, 1.3276745080947876, 1.6518287658691406, 2.2877464294433594, 1.8827145099639893, 1.7006149291992188, 2.3836348056793213, 2.698089599609375, 1.3948321342468262, 1.8983603715896606, 1.9773067235946655, 2.30149507522583, 2.5041868686676025, 2.1858513355255127, 1.1552284955978394, 2.0618934631347656, 1.342185378074646, 2.4183707237243652, 158.49525451660156, 147.8880615234375, 213.15167236328125, 204.6678924560547, 97.72970581054688, 195.3605499267578, 266.65155029296875, 141.56314086914062, 42.92942428588867, 117.12632751464844, 147.03927612304688, 214.0154571533203, 192.6488037109375, 213.16905212402344, 347.7693786621094, 186.0567169189453, 118.4891586303711, 241.39952087402344, 186.9102325439453, 204.5867919921875, 118.70275115966797, 149.04335021972656, 139.299072265625, 27.58245849609375, 163.64535522460938, 117.04792785644531, 329.17413330078125, 175.45538330078125, 32.3099365234375, 93.32569885253906, 135.00611877441406, 343.77569580078125, 286.802734375, 173.7304229736328, 160.74420166015625, 33.73421096801758, 69.05229187011719, 45.8797607421875, 201.34222412109375, 40.218994140625, 30.3154296875, 111.15130615234375, 178.7410430908203, 110.41852569580078, 174.8983612060547, 277.419921875, 108.19269561767578, 253.6097412109375, 113.306640625, 44.0875244140625, 190.6419677734375, 193.54031372070312, 55.404300689697266, 45.38808059692383, 110.7364501953125, 31.178861618041992, 315.1174011230469, 31.686920166015625, 122.6292953491211, 172.52276611328125, 224.19293212890625, 166.0333709716797, 287.52081298828125, 119.75196075439453, 134.7702178955078, 81.74627685546875, 274.8709716796875, 67.91867065429688, 230.20733642578125, 58.070068359375, 165.48355102539062, 176.94778442382812, 264.9064636230469, 65.53414916992188, 46.32341384887695, 23.846435546875, 31.682010650634766, 39.37493896484375, 203.03868103027344, 253.98362731933594, 103.657470703125, 105.7591552734375, 213.3835906982422, 239.37646484375, 273.4386291503906, 164.8826141357422, 145.64772033691406, 143.33746337890625, 71.430908203125, 73.4041748046875, 210.70664978027344, 47.56330871582031, 55.369964599609375, 172.4937286376953, 230.765380859375, 147.93223571777344, 202.1995086669922, 94.484130859375, 231.60897827148438, 185.9462432861328, 30.00271224975586, 97.58487701416016, 155.5620880126953, 108.14595794677734, 153.2451171875, 139.62811279296875, 209.82681274414062, 189.54296875, 189.7391815185547, 282.56793212890625, 124.8461685180664, 272.17236328125, 77.72005462646484, 109.28704833984375, 65.39173889160156, 281.6627197265625, 197.7846221923828, 145.1481475830078, 237.6522979736328, 43.962703704833984, 273.1378173828125, 227.01104736328125, 180.7266387939453, 145.21315002441406, 152.36293029785156, 108.125732421875, 150.62306213378906, 174.4336700439453, 112.55773162841797, 97.26380920410156, 91.1983642578125, 231.0310516357422, 120.17222595214844, 76.87139129638672, 61.59687423706055, 116.76190185546875, 65.989013671875, 95.95275115966797, 76.46177673339844, 193.985107421875, 79.73324584960938, 58.590576171875, 79.92192840576172, 55.57693099975586, 103.5745849609375, 197.0065460205078, 80.01753997802734, 78.83694458007812, 118.44857788085938, 79.9312744140625, 214.7240753173828, 263.97943115234375, 36.902099609375, 58.5390625, 218.0409698486328, 207.9550018310547, 241.68408203125, 194.52798461914062, 286.392333984375, 85.3612060546875, 145.8704833984375, 66.96875, 56.19636154174805, 29.2418212890625, 155.24375915527344, 268.6134338378906, 122.49181365966797, 31.30743408203125, 50.18035888671875, 90.06157684326172, 36.74927520751953, 123.14554595947266, 142.71771240234375, 75.3485107421875, 191.48828125, 263.91168212890625, 115.69126892089844, 177.83311462402344, 107.8232421875, 103.52570343017578, 200.32159423828125, 175.1118927001953, 213.7430419921875, 67.17774200439453, 290.20068359375, 131.137939453125, 54.2711067199707, 98.8621826171875, 117.10247802734375, 236.2694549560547, 173.1891632080078, 45.111053466796875, 58.67626953125, 263.8038330078125, 65.33403778076172, 106.06117248535156, 90.53226470947266, 249.89984130859375, 62.588134765625, 83.85501861572266, 146.2485809326172, 86.0176773071289, 128.00672912597656, 59.28092956542969, 161.50306701660156, 197.0576934814453, 155.42132568359375, 112.00093841552734, 247.63323974609375, 139.77157592773438, 113.01866912841797, 43.9986572265625, 215.1962432861328, 57.038631439208984, 134.9296112060547, 305.86529541015625, 336.89556884765625, 280.8524169921875, 56.372859954833984, 174.9498748779297, 99.11395263671875, 74.7215347290039, 53.88709259033203, 59.814544677734375, 132.24066162109375, 49.17485427856445, 200.8327178955078, 152.6450958251953, 197.42578125, 42.276580810546875, 94.39642333984375, 50.403865814208984, 182.02835083007812, 397.1778869628906, 65.96255493164062, 173.8934326171875, 101.19647216796875, 47.586917877197266, 135.12380981445312, 130.94540405273438, 157.27886962890625, 70.43548583984375, 90.03604888916016, 180.4537811279297, 133.45880126953125, 169.4597625732422, 69.0726089477539, 112.36688232421875, 81.49285888671875, 119.02324676513672, 80.0682373046875, 67.71478271484375, 61.7491455078125, 127.51761627197266, 121.40689086914062, 33.74665451049805, 125.28595733642578, 207.9326171875, 213.00604248046875, 43.31545639038086, 37.17603302001953, 217.91140747070312, 63.09693145751953, 293.1252136230469, 306.29339599609375, 36.80080795288086, 91.3583984375, 34.554443359375, 262.22515869140625, 51.0267333984375, 29.697633743286133, 144.3742218017578, 224.61546325683594, 144.48928833007812, 158.13870239257812, 186.05691528320312, 234.18768310546875, 264.4736022949219, 58.105281829833984, 84.80043029785156, 100.90601348876953, 163.65708923339844, 287.23187255859375, 44.15127182006836, 144.76023864746094, 40.982177734375, 186.7802276611328, 119.20635223388672, 123.28058624267578, 136.36839294433594, 118.65496826171875, 73.47246551513672, 107.74462890625, 53.79730224609375, 49.093505859375, 223.2157440185547, 192.11045837402344, 498.2518615722656, 135.43539428710938, 45.080814361572266, 2.568711996078491, 1.2451403141021729, 1.614203929901123, 3.6595659255981445, 2.426112413406372, 2.444016695022583, 2.439295530319214, 2.4993491172790527, 2.7890655994415283, 2.1945595741271973, 3.8554656505584717, 1.7864031791687012, 3.001922607421875, 3.4526748657226562, 1.9005969762802124, 1.304732322692871, 1.1411809921264648, 3.43522572517395, 2.269620656967163, 2.334670066833496, 2.099066972732544, 2.146009683609009, 2.3166723251342773, 2.4537129402160645, 1.633362054824829, 2.715718984603882, 2.096789836883545, 2.2485849857330322, 2.211422920227051, 2.3105790615081787, 2.087315559387207, 2.2229700088500977, 3.072039842605591, 3.7309200763702393, 1.7873268127441406, 2.714127779006958, 3.335211753845215, 2.088395118713379, 3.598508834838867, 3.019131898880005, 2.1094789505004883, 2.8460681438446045, 3.1021504402160645, 2.526852607727051, 1.862488031387329, 1.3016430139541626, 2.3719253540039062, 2.7548632621765137, 2.0686264038085938, 3.0282528400421143, 2.134676218032837, 2.1637704372406006, 1.6491063833236694, 1.8444374799728394, 3.159318685531616, 2.0159943103790283, 2.529294013977051, 2.789788246154785, 3.1996490955352783, 1.999571442604065, 3.3889360427856445, 3.6319618225097656, 2.3702688217163086, 2.7210659980773926, 1.6367549896240234, 2.4004602432250977, 1.6029551029205322, 3.2744016647338867, 2.231367349624634, 1.6083344221115112, 2.1725964546203613, 2.0902299880981445, 1.8106380701065063, 2.710369110107422, 2.1482057571411133, 2.6743762493133545, 2.1542487144470215, 2.3633923530578613, 2.6112701892852783, 2.3708903789520264, 2.5744314193725586, 3.3523740768432617, 2.132577419281006, 1.855507731437683, 2.9666337966918945, 2.3186678886413574, 2.10284686088562, 1.8509206771850586, 1.1191271543502808, 1.8994628190994263, 1.0282387733459473, 1.8457649946212769, 1.6660664081573486, 3.0223283767700195, 2.460261344909668, 3.042677640914917, 1.3766741752624512, 4.374938488006592, 2.57443904876709, 1.7582669258117676, 3.611727714538574, 2.162865161895752, 2.371516466140747, 2.417501211166382, 2.2576239109039307, 2.8967010974884033, 2.5020265579223633, 1.7942113876342773, 2.848869562149048, 1.630226969718933, 2.0578763484954834, 2.2649753093719482, 2.24454402923584, 3.420233726501465, 2.242293357849121, 1.4504159688949585, 2.4795467853546143, 2.3375120162963867, 3.220522880554199, 2.6225860118865967, 3.0706121921539307, 2.6113367080688477, 2.6191766262054443, 3.086611270904541, 2.4475698471069336, 2.492305040359497, 2.30853533744812, 3.7290055751800537, 2.0744504928588867, 1.661457896232605, 2.2500057220458984, 2.8132410049438477, 2.1166317462921143, 1.6888532638549805, 2.264159917831421, 2.125840187072754, 2.2529919147491455, 2.143650770187378, 2.313878059387207, 2.2999887466430664, 1.7411545515060425, 2.211857795715332, 3.6360976696014404, 2.387423038482666, 1.7841763496398926, 1.908394694328308, 2.621882200241089, 2.6220922470092773, 3.5671684741973877, 3.5133330821990967, 1.92638099193573, 2.894730806350708, 2.9740703105926514, 1.377547264099121, 2.0898678302764893, 2.266139030456543, 1.5219497680664062, 2.472925901412964, 3.170581102371216, 3.025988817214966, 2.427435874938965, 2.199176788330078, 1.9912900924682617, 1.5891715288162231, 2.509037971496582, 2.8966331481933594, 3.4216277599334717, 2.0294995307922363, 2.8218719959259033, 2.0699779987335205, 1.2864755392074585, 2.4376678466796875, 2.916027784347534, 1.6559327840805054, 1.8536797761917114, 1.8189153671264648, 2.273310661315918, 2.1737191677093506, 2.8583691120147705, 3.7953450679779053, 3.151900053024292, 2.173614025115967, 3.440446138381958, 1.563184142112732, 2.7760565280914307, 1.7453454732894897, 1.8376542329788208, 1.3643815517425537, 2.8862316608428955, 2.184148073196411, 3.3421850204467773, 1.810575008392334, 1.7283622026443481, 1.509047508239746, 2.3309926986694336, 3.340681791305542, 1.870003581047058, 3.951542854309082, 3.2264723777770996, 2.1745357513427734, 2.4111642837524414, 3.1340672969818115, 2.158665180206299, 1.6123456954956055, 1.622424840927124, 1.5099624395370483, 2.2094459533691406, 2.928131103515625, 2.09294056892395, 2.0648610591888428, 1.9515312910079956, 2.4087932109832764, 2.138209342956543, 1.7048559188842773, 3.47823429107666, 1.369901418685913, 1.6676303148269653, 2.5612194538116455, 1.664750337600708, 1.9434292316436768, 2.3025338649749756, 2.318953514099121, 3.320064067840576, 3.6239922046661377, 4.171936988830566, 2.7183661460876465, 3.73691463470459, 3.2125957012176514, 3.1035842895507812, 2.233168601989746, 2.5719733238220215, 2.2954800128936768, 1.644753336906433, 2.1385316848754883, 2.6498937606811523, 2.1008214950561523, 3.1427643299102783, 1.8641325235366821, 2.8081886768341064, 1.9400739669799805, 1.888142466545105, 1.900445818901062, 2.6054887771606445, 2.0327577590942383, 2.0327863693237305, 1.7075148820877075, 1.5160709619522095, 3.2144691944122314, 2.692279100418091, 2.962636947631836, 1.6189724206924438, 2.5281479358673096, 2.4999706745147705, 3.462958574295044, 2.4712636470794678, 1.9073916673660278, 2.272887706756592, 2.078153371810913, 1.803183913230896, 1.322139859199524, 1.740681529045105, 2.6927521228790283, 2.8145339488983154, 1.3886065483093262, 3.709479331970215, 2.546328544616699, 3.3448598384857178, 1.6000527143478394, 1.995982050895691, 2.436251401901245, 1.9752167463302612, 2.231766700744629, 1.8922775983810425, 2.258387565612793, 2.932037830352783, 2.651728868484497, 2.356999158859253, 1.9776126146316528, 2.1105337142944336, 3.5073535442352295, 1.9276885986328125, 2.5855746269226074, 3.285062789916992, 1.7922028303146362, 2.464911460876465, 2.644320011138916, 3.21488094329834, 3.6777849197387695, 2.0775270462036133, 2.482154130935669, 3.812192916870117, 2.6387131214141846, 2.9265594482421875, 2.487149238586426, 2.4258477687835693, 1.133583903312683, 3.0166378021240234, 3.6450276374816895, 1.9505127668380737, 3.145242214202881, 0.21857360005378723, 0.15195246040821075, 0.16987772285938263, 0.25579679012298584, 0.27883630990982056, 0.12252040952444077, 0.22648663818836212, 0.19424282014369965, 0.24311885237693787, 0.23068857192993164, 0.1688908487558365, 0.2168697863817215, 0.20898738503456116, 0.24109633266925812, 0.1630641520023346, 0.22693988680839539, 0.14756566286087036, 0.17878620326519012, 0.2203737199306488, 0.18738576769828796, 0.22614294290542603, 0.2655266523361206, 0.21684476733207703, 0.1969251185655594, 0.2825452387332916, 0.17859309911727905, 0.22571006417274475, 0.22364991903305054, 0.24591343104839325, 0.20735414326190948, 0.1738262176513672, 0.16494624316692352, 0.12743642926216125, 0.19028446078300476, 0.23766691982746124, 0.20623309910297394, 0.18721166253089905, 0.21317683160305023, 0.19625574350357056, 0.201676607131958, 0.17091314494609833, 0.16496099531650543, 0.22615936398506165, 0.17117543518543243, 0.23910972476005554, 0.18338027596473694, 0.2574533522129059, 0.19827891886234283, 0.20202700793743134, 0.1512884497642517, 0.22897914052009583, 0.18949809670448303, 0.211994931101799, 0.24097800254821777, 0.2240702211856842, 0.2228337824344635, 0.20656180381774902, 0.21580982208251953, 0.217848539352417, 0.1836024820804596, 0.19014224410057068, 0.14778394997119904, 0.2129206359386444, 0.18929149210453033, 0.21412955224514008, 0.15021578967571259, 0.21119028329849243, 0.1593959927558899, 0.16837000846862793, 0.1981019228696823, 0.15892323851585388, 0.1908576935529709, 0.2174537628889084, 0.20787513256072998, 0.13845372200012207, 0.2150299996137619, 0.17733818292617798, 0.10198289901018143, 0.2405107319355011, 0.15720711648464203, 0.20290519297122955, 0.1666107177734375, 0.20191256701946259, 0.1961248368024826, 0.22913356125354767, 0.22150547802448273, 0.2232879400253296, 0.2211368829011917, 0.19761943817138672, 0.21306848526000977, 0.17959348857402802, 0.2388553023338318, 0.19644220173358917, 0.18953952193260193, 0.22132423520088196, 0.16646899282932281, 0.2130698710680008, 0.14728228747844696, 0.16656558215618134, 0.18942877650260925, 0.2519860863685608, 0.1511087715625763, 0.18671955168247223, 0.19679343700408936, 0.1873725801706314, 0.1566087305545807, 0.15983270108699799, 0.20215660333633423, 0.17067930102348328, 0.2436809539794922, 0.18152973055839539, 0.23889577388763428, 0.18360330164432526, 0.1646503210067749, 0.19630563259124756, 0.12167002260684967, 0.21511699259281158, 0.20267727971076965, 0.16095662117004395, 0.22052203118801117, 0.19634543359279633, 0.1870994120836258, 0.1645684540271759, 0.1961117535829544, 0.18993552029132843, 0.1861611157655716, 0.18391454219818115, 0.2237296849489212, 0.2453455626964569, 0.21621428430080414, 0.26071107387542725, 0.12049395591020584, 0.20532828569412231, 0.19574566185474396, 0.2252451330423355, 0.2834530174732208, 0.15140412747859955, 0.2076377421617508, 0.23573946952819824, 0.13764458894729614, 0.23480403423309326, 0.24859057366847992, 0.23392802476882935, 0.1892356276512146, 0.16649161279201508, 0.24485206604003906, 0.20944221317768097, 0.20918793976306915, 0.1978764832019806, 0.12948547303676605, 0.16781651973724365, 0.20198120176792145, 0.19527673721313477, 0.16864272952079773, 0.22204938530921936, 0.18053634464740753, 0.23910503089427948, 0.15944941341876984, 0.16252098977565765, 0.20416419208049774, 0.20292997360229492, 0.2154255211353302, 0.21291950345039368, 0.19697321951389313, 0.19290399551391602, 0.1882624626159668, 0.1703711599111557, 0.2178209275007248, 0.23064589500427246, 0.2342415750026703, 0.1823490411043167, 0.15613511204719543, 0.21465428173542023, 0.1746206283569336, 0.1818448156118393, 0.16771304607391357, 0.12477966398000717, 0.15457813441753387, 0.18832679092884064, 0.1917184740304947, 0.26252391934394836, 0.14781515300273895, 0.23920957744121552, 0.1748264580965042, 0.2476900815963745, 0.217564657330513, 0.16287845373153687, 0.2029675990343094, 0.25864776968955994, 0.2229161560535431, 0.2438081055879593, 0.22791069746017456, 0.18492740392684937, 0.23650579154491425, 0.1457318812608719, 0.2551799416542053, 0.23645861446857452, 0.220063716173172, 0.1795225888490677, 0.275539368391037, 0.23191958665847778, 0.21008171141147614, 0.21251991391181946, 0.2569241225719452, 0.22185343503952026, 0.2239258587360382, 0.15880274772644043, 0.2740575969219208, 0.2759484052658081, 0.16088908910751343, 0.1349819153547287, 0.14062826335430145, 0.1860978901386261, 0.1806231290102005, 0.23172709345817566, 0.21193020045757294, 0.21446000039577484, 0.22228585183620453, 0.19728414714336395, 0.22662152349948883, 0.22113145887851715, 0.18090060353279114, 0.16298840939998627, 0.19630298018455505, 0.18736398220062256, 0.2445041388273239, 0.2079087793827057, 0.1422637403011322, 0.19636714458465576, 0.20466841757297516, 0.2546306252479553, 0.2471301257610321, 0.2307097166776657, 0.1841784566640854, 0.19468681514263153, 0.17554453015327454, 0.2476637214422226, 0.21913644671440125, 0.1626577526330948, 0.17090937495231628, 0.2070988416671753, 0.12234685570001602, 0.20981073379516602, 0.2281026542186737, 0.1341785192489624, 0.09415187686681747, 0.14375367760658264, 0.16808345913887024, 0.2348240613937378, 0.20502342283725739, 0.14698481559753418, 0.19800788164138794, 0.23744887113571167, 0.24213539063930511, 0.18760572373867035, 0.18702629208564758, 0.1699092835187912, 0.1953895092010498, 0.11403012275695801, 0.22505348920822144, 0.18355925381183624, 0.21648359298706055, 0.1643185019493103, 0.173496276140213, 0.2584057152271271, 0.25345757603645325, 0.14391867816448212, 0.22104597091674805, 0.1771547496318817, 0.2188190221786499, 0.2888910472393036, 0.27509838342666626, 0.2105875164270401, 0.16814425587654114, 0.1620449274778366, 0.25376245379447937, 0.1468549370765686, 0.20545844733715057, 0.2519020140171051, 0.1856585443019867, 0.17463278770446777, 0.1985679566860199, 0.24159656465053558, 0.229446142911911, 0.1994674652814865, 0.168777734041214, 0.20795413851737976, 0.1721179485321045, 0.1960507482290268, 0.14848396182060242, 0.1633908748626709, 0.2061987966299057, 0.27085667848587036, 0.21253331005573273, 0.20719584822654724, 0.18403853476047516, 0.18909808993339539, 0.24829670786857605, 0.22255168855190277, 0.25047916173934937, 1.5929467678070068, 2.6281192302703857, 2.027602195739746, 2.1511518955230713, 1.5914192199707031, 1.078687071800232, 1.3061326742172241, 1.9165847301483154, 1.2291619777679443, 2.2168493270874023, 2.6185317039489746, 2.275198221206665, 1.7850608825683594, 1.5800775289535522, 0.9794668555259705, 2.0594873428344727, 1.795713186264038, 1.4622360467910767, 2.2295243740081787, 1.561661958694458, 2.323869228363037, 2.686084508895874, 1.8744721412658691, 1.4431835412979126, 1.506427526473999, 1.4662166833877563, 2.870900869369507, 2.3761351108551025, 1.9752076864242554, 1.6650023460388184, 1.5307505130767822, 1.3505642414093018, 2.472748279571533, 2.4365103244781494, 1.931862473487854, 1.2299931049346924, 1.560680627822876, 2.115677833557129, 2.059481382369995, 1.4861313104629517, 1.7075086832046509, 1.2400906085968018, 1.444038987159729, 2.411102533340454, 1.0688998699188232, 1.1596463918685913, 2.4932031631469727, 2.5212132930755615, 1.8502428531646729, 2.2490086555480957, 1.58147132396698, 1.457094430923462, 3.190258741378784, 1.9573017358779907, 2.1776180267333984, 1.7371517419815063, 2.197545051574707, 1.465088129043579, 2.086678981781006, 2.403557777404785, 1.780145525932312, 1.936421275138855, 2.7648837566375732, 2.3533382415771484, 1.8489338159561157, 2.2845089435577393, 2.0134520530700684, 2.374969482421875, 1.7721571922302246, 1.7810245752334595, 2.8977153301239014, 1.598966360092163, 1.6574745178222656, 1.9712705612182617, 1.9777902364730835, 2.264892578125, 2.203770875930786, 1.8131273984909058, 2.7001919746398926, 0.9808648228645325, 1.972821593284607, 1.9377539157867432, 1.238483190536499, 2.092341661453247, 1.350152850151062, 1.6857656240463257, 0.8321183323860168, 1.9445186853408813, 1.5004730224609375, 2.630308151245117, 2.2170636653900146, 2.1733736991882324, 1.8115196228027344, 1.5684868097305298, 2.1183393001556396, 2.902317762374878, 2.0256028175354004, 1.9997901916503906, 2.336686134338379, 1.832522988319397, 2.8154406547546387, 1.618145227432251, 2.133824348449707, 2.7579169273376465, 2.941986083984375, 2.566232442855835, 2.3413596153259277, 1.316192626953125, 1.6472381353378296, 1.7514666318893433, 1.5674692392349243, 2.931262731552124, 1.194334864616394, 2.1158831119537354, 2.025404930114746, 1.6296119689941406, 1.469152808189392, 1.6523847579956055, 1.5221633911132812, 1.3920093774795532, 2.178546905517578, 2.355800151824951, 2.3688647747039795, 3.0445785522460938, 1.6599825620651245, 2.1598851680755615, 1.4612528085708618, 2.555077075958252, 1.144377589225769, 1.4222580194473267, 1.6794359683990479, 1.44502592086792, 1.5551667213439941, 1.8531709909439087, 1.6074578762054443, 1.3577264547348022, 1.7216933965682983, 2.370386838912964, 2.3019864559173584, 2.084118366241455, 2.142514944076538, 3.051086902618408, 1.580599308013916, 3.3880085945129395, 1.9036457538604736, 1.4837409257888794, 2.6771481037139893, 2.8603386878967285, 1.7433937788009644, 2.491959571838379, 1.7463792562484741, 2.3265559673309326, 0.9854094982147217, 2.4350576400756836, 1.1956515312194824, 2.4289450645446777, 2.0263216495513916, 1.7544283866882324, 1.3097491264343262, 1.8877557516098022, 1.696520447731018, 1.6437422037124634, 1.746885061264038, 1.0918364524841309, 1.804028034210205, 1.9542535543441772, 1.7757656574249268, 1.9080404043197632, 1.8590679168701172, 1.5926378965377808, 1.4830117225646973, 1.3664089441299438, 3.0049002170562744, 2.155383586883545, 1.9589647054672241, 1.64835786819458, 2.3094372749328613, 2.2156312465667725, 1.905869960784912, 1.9107375144958496, 1.2454020977020264, 2.0439205169677734, 1.6201249361038208, 2.2204535007476807, 1.639276385307312, 1.7817590236663818, 2.135096311569214, 1.8631905317306519, 2.190598964691162, 1.3591728210449219, 1.376242995262146, 2.617382764816284, 1.8395867347717285, 1.950669765472412, 2.010826826095581, 2.3707094192504883, 1.9691263437271118, 1.4508171081542969, 2.5999245643615723, 2.281087875366211, 1.870499849319458, 2.1311662197113037, 2.1624755859375, 2.515652656555176, 2.453734874725342, 1.4804264307022095, 3.198432207107544, 3.30047345161438, 1.5945123434066772, 1.2469544410705566, 1.557733416557312, 2.06894850730896, 1.5132757425308228, 1.7485897541046143, 2.37565279006958, 1.9051424264907837, 2.2621474266052246, 1.2052996158599854, 1.5987358093261719, 2.936328172683716, 3.011707067489624, 1.793763279914856, 1.2874104976654053, 3.2936980724334717, 1.6599031686782837, 2.2127623558044434, 2.7072596549987793, 1.08559250831604, 2.6603100299835205, 1.7768921852111816, 1.822011947631836, 2.1593594551086426, 1.3334640264511108, 1.6846270561218262, 2.7678844928741455, 1.9433567523956299, 1.1413183212280273, 2.560539484024048, 1.7317301034927368, 2.010939359664917, 1.9171655178070068, 1.9317306280136108, 2.177328109741211, 2.292029619216919, 2.1051690578460693, 1.4318811893463135, 1.4901221990585327, 2.1534879207611084, 1.9182366132736206, 1.7588820457458496, 1.884643793106079, 1.6463019847869873, 2.8394579887390137, 1.5108000040054321, 2.1039087772369385, 1.7618976831436157, 1.5653715133666992, 1.3822762966156006, 1.5631195306777954, 2.2248082160949707, 2.4935359954833984, 1.9692115783691406, 2.1608569622039795, 2.4948136806488037, 1.831923484802246, 1.5516152381896973, 1.7122300863265991, 1.7344884872436523, 2.500922679901123, 1.453363060951233, 2.371764659881592, 2.934779644012451, 1.776990294456482, 1.445967674255371, 1.5004370212554932, 1.3174394369125366, 2.1856770515441895, 1.6203958988189697, 1.3336607217788696, 1.8915624618530273, 1.8102169036865234, 2.3476550579071045, 2.2615747451782227, 1.2113399505615234, 2.4095544815063477, 2.474012613296509, 1.3048808574676514, 2.2857580184936523, 1.3293142318725586, 1.3766047954559326, 1.9414352178573608, 2.612520694732666, 1.7747433185577393, 1.3176536560058594, 2.7793965339660645, 2.2002882957458496, 1.7778774499893188, 1.6497939825057983, 1.612199306488037, 3.5590198040008545, 102.89398193359375, 137.03932189941406, 241.1713409423828, 62.91845703125, 102.71392059326172, 129.7370147705078, 122.30201721191406, 205.4053497314453, 77.84014129638672, 268.5458068847656, 83.56075286865234, 69.80581665039062, 93.8680419921875, 65.56729125976562, 132.56031799316406, 86.28203582763672, 114.11402893066406, 226.53578186035156, 127.67681121826172, 174.9303436279297, 108.50568389892578, 119.64102935791016, 62.77740478515625, 78.96480560302734, 36.07423782348633, 239.92300415039062, 164.7638702392578, 233.9020233154297, 30.44476318359375, 291.8635559082031, 152.0218505859375, 149.9267578125, 200.1216583251953, 138.72918701171875, 47.6993408203125, 55.06892776489258, 166.5167999267578, 193.16555786132812, 65.94873046875, 193.1658935546875, 219.95379638671875, 286.2881164550781, 113.0419921875, 143.60585021972656, 88.57147216796875, 35.49615478515625, 94.19904327392578, 225.51690673828125, 256.15496826171875, 113.3707275390625, 246.0327606201172, 309.5291442871094, 155.00982666015625, 617.3018798828125, 419.5994567871094, 71.59721374511719, 120.22521209716797, 303.76165771484375, 161.00274658203125, 147.06671142578125, 93.5399398803711, 140.273681640625, 257.41448974609375, 136.01861572265625, 257.20709228515625, 87.01898193359375, 45.99516677856445, 197.82980346679688, 260.43878173828125, 100.04064178466797, 58.308719635009766, 171.09249877929688, 398.7308654785156, 94.16864013671875, 244.3824920654297, 111.25692749023438, 124.4681396484375, 202.0832061767578, 341.14263916015625, 60.952938079833984, 64.87238311767578, 29.640207290649414, 136.60748291015625, 31.07855224609375, 125.4410400390625, 113.1131591796875, 49.29842758178711, 352.19287109375, 56.03070068359375, 50.2636604309082, 141.82839965820312, 129.58770751953125, 201.1468505859375, 54.96506881713867, 150.74183654785156, 106.43490600585938, 136.00547790527344, 71.50244140625, 47.48493194580078, 172.83843994140625, 391.1684265136719, 58.610595703125, 45.741424560546875, 26.10059928894043, 113.58394622802734, 110.880615234375, 271.094970703125, 264.2767333984375, 151.59429931640625, 396.7677307128906, 69.30913543701172, 31.2413330078125, 28.382781982421875, 35.9820556640625, 32.76171875, 55.03110885620117, 147.89170837402344, 68.11102294921875, 100.44029235839844, 202.12823486328125, 274.9208679199219, 189.16233825683594, 37.104774475097656, 220.44569396972656, 252.30191040039062, 223.1778106689453, 47.158935546875, 105.53533935546875, 58.128074645996094, 47.05166244506836, 169.60121154785156, 84.2039566040039, 344.6223449707031, 166.74473571777344, 181.1170654296875, 284.27105712890625, 29.109012603759766, 114.7533950805664, 54.60906982421875, 165.614013671875, 250.2481231689453, 33.31756591796875, 110.72101593017578, 121.2878646850586, 249.80638122558594, 121.60931396484375, 232.3939208984375, 193.11962890625, 69.3795166015625, 132.33987426757812, 164.7644500732422, 165.79989624023438, 166.7674560546875, 39.85681915283203, 114.83696746826172, 31.831787109375, 128.62176513671875, 91.43841552734375, 218.14959716796875, 64.00005340576172, 118.00841522216797, 171.96420288085938, 158.25115966796875, 154.29562377929688, 136.57177734375, 145.138427734375, 90.46488189697266, 82.40113067626953, 146.8653106689453, 420.4812927246094, 175.07748413085938, 112.4631118774414, 131.75205993652344, 77.571533203125, 97.7276611328125, 110.0919189453125, 228.3701934814453, 104.70195770263672, 224.71405029296875, 174.4432830810547, 49.8232421875, 92.08785247802734, 206.9060516357422, 105.2493896484375, 144.18597412109375, 180.7283172607422, 56.99990463256836, 136.00103759765625, 243.4706268310547, 190.99082946777344, 241.9554901123047, 127.10753631591797, 236.48162841796875, 118.34310150146484, 244.44140625, 65.7108154296875, 43.896575927734375, 183.9439239501953, 60.58953857421875, 63.69915771484375, 93.67993927001953, 51.55220031738281, 67.607666015625, 151.8116912841797, 151.59848022460938, 180.7410125732422, 37.22358322143555, 51.94598388671875, 69.62014770507812, 56.14447021484375, 114.57980346679688, 34.47382736206055, 102.98009490966797, 139.07818603515625, 41.80232238769531, 56.863094329833984, 177.302490234375, 98.42264556884766, 214.1782989501953, 161.68634033203125, 202.9517364501953, 55.44770431518555, 358.7604675292969, 171.59274291992188, 79.08447265625, 111.66384887695312, 152.1175537109375, 83.08436584472656, 110.62071990966797, 243.10662841796875, 30.907073974609375, 119.3558578491211, 205.0252227783203, 49.35500717163086, 101.8792724609375, 143.37147521972656, 191.3357696533203, 114.30615234375, 119.56623840332031, 237.7810516357422, 244.86541748046875, 90.95619201660156, 219.5834503173828, 419.2425537109375, 157.81253051757812, 169.4207763671875, 139.9381866455078, 279.8720397949219, 80.68045806884766, 220.5447235107422, 115.7126235961914, 277.5740966796875, 53.1964111328125, 70.63508605957031, 49.597469329833984, 63.4608154296875, 191.2510528564453, 108.0452880859375, 56.328182220458984, 233.3543701171875, 337.212646484375, 41.51773452758789, 91.79448699951172, 119.5050048828125, 143.91612243652344, 297.8357238769531, 196.8214874267578, 245.0530548095703, 180.5926055908203, 38.79241943359375, 59.07659912109375, 210.9115753173828, 120.64691162109375, 84.2627944946289, 283.4444580078125, 140.9871826171875, 41.087158203125, 72.15740966796875, 93.85836029052734, 59.31555938720703, 80.20973205566406, 109.20152282714844, 147.9676971435547, 255.3226318359375, 32.06610107421875, 37.22971725463867, 156.1376953125, 199.625, 43.25472640991211, 121.85729217529297, 77.51326751708984, 99.95853424072266, 100.548583984375, 84.50957489013672, 199.3452911376953, 165.8917999267578, 167.39620971679688, 248.08436584472656, 170.1365966796875, 424.36041259765625, 1.7675942182540894, 1.716878056526184, 2.9296483993530273, 3.0964174270629883, 2.1288256645202637, 1.5701371431350708, 2.376133918762207, 2.744246244430542, 1.1769757270812988, 2.7785065174102783, 2.6293158531188965, 3.0402684211730957, 2.4626758098602295, 3.203770637512207, 3.514329195022583, 1.7761459350585938, 2.6021728515625, 2.715346097946167, 1.7026244401931763, 2.03897762298584, 2.5465545654296875, 3.7637388706207275, 2.3938703536987305, 3.219632387161255, 2.9785051345825195, 1.8239482641220093, 3.1406261920928955, 2.463475227355957, 2.2403743267059326, 3.287276029586792, 3.9436352252960205, 3.1274349689483643, 2.6625378131866455, 2.8823437690734863, 1.7727309465408325, 2.533024787902832, 2.949688673019409, 2.6479082107543945, 2.9182116985321045, 3.1592674255371094, 2.2010223865509033, 1.095901370048523, 2.539841651916504, 3.0890228748321533, 3.0261242389678955, 2.642888069152832, 2.177476167678833, 3.455366849899292, 2.247769355773926, 2.8053979873657227, 2.6195287704467773, 2.3905131816864014, 1.6674001216888428, 3.769151449203491, 2.8351902961730957, 1.747721791267395, 3.548966646194458, 3.5744946002960205, 2.5992138385772705, 2.6921515464782715, 2.4349069595336914, 2.2475907802581787, 2.0994091033935547, 2.9117283821105957, 2.1809396743774414, 2.608135938644409, 2.1114213466644287, 1.4489469528198242, 1.9964089393615723, 1.4813003540039062, 3.4312736988067627, 2.8778088092803955, 1.921689510345459, 2.0864267349243164, 2.492558479309082, 2.2322723865509033, 3.6931397914886475, 2.251018524169922, 2.2417802810668945, 2.613330602645874, 1.8947685956954956, 2.990682363510132, 1.780348300933838, 2.2203288078308105, 1.758126139640808, 2.9225926399230957, 2.8247954845428467, 1.672116994857788, 2.262444257736206, 2.367947578430176, 1.818124532699585, 3.1768417358398438, 1.6697722673416138, 2.648494243621826, 3.394598960876465, 3.0317463874816895, 1.2087821960449219, 1.9956978559494019, 3.352065324783325, 3.442486524581909, 2.8057525157928467, 2.19913649559021, 3.1239006519317627, 2.8457558155059814, 1.9067400693893433, 2.7346832752227783, 1.0248873233795166, 3.542757987976074, 2.482293128967285, 2.4425604343414307, 2.3409183025360107, 1.5527563095092773, 3.332707405090332, 2.2418060302734375, 2.2370636463165283, 2.237719774246216, 2.144902229309082, 2.826207399368286, 2.774522066116333, 2.690267324447632, 2.3548920154571533, 2.309891700744629, 2.285564422607422, 3.3606200218200684, 1.3468213081359863, 2.191206932067871, 2.2653284072875977, 2.422004461288452, 1.705132246017456, 2.0015344619750977, 2.067556381225586, 2.665400981903076, 2.7200286388397217, 1.4552582502365112, 1.7699291706085205, 2.452193260192871, 2.218493938446045, 2.9109599590301514, 2.871671676635742, 3.740544557571411, 2.230626106262207, 2.233086585998535, 3.4626576900482178, 1.9642494916915894, 1.4957609176635742, 2.5410423278808594, 1.572835922241211, 3.337771415710449, 1.9557749032974243, 1.857131004333496, 2.0343847274780273, 2.650324583053589, 3.092496156692505, 1.623377799987793, 3.577112913131714, 3.469855308532715, 3.284919023513794, 2.69228458404541, 3.839128255844116, 3.1427857875823975, 2.3144235610961914, 2.6441943645477295, 2.484522819519043, 3.4338314533233643, 2.7739458084106445, 1.7288203239440918, 1.5141782760620117, 1.6107244491577148, 2.6771953105926514, 2.730062246322632, 2.836113214492798, 2.19499135017395, 2.6797735691070557, 3.172093629837036, 2.5437233448028564, 3.2418456077575684, 2.4688596725463867, 3.2489092350006104, 2.3565893173217773, 3.640216588973999, 2.338366746902466, 2.050245523452759, 3.7341063022613525, 2.0965416431427, 3.0610339641571045, 1.4045944213867188, 2.1481010913848877, 2.20351243019104, 2.5458261966705322, 2.795766830444336, 2.431833028793335, 3.4821934700012207, 1.9031695127487183, 4.01411771774292, 3.0167644023895264, 3.0744965076446533, 1.3095998764038086, 2.6899406909942627, 2.5907177925109863, 2.2133989334106445, 3.907207489013672, 3.8903093338012695, 1.840632438659668, 2.3957643508911133, 2.898693799972534, 1.8798818588256836, 2.7623496055603027, 2.8124377727508545, 3.18375563621521, 3.0843911170959473, 2.4710474014282227, 2.5591793060302734, 2.2887816429138184, 3.200859546661377, 2.9137284755706787, 1.8146390914916992, 2.3621132373809814, 1.6040962934494019, 1.8884893655776978, 1.5833481550216675, 3.403512716293335, 3.821267604827881, 2.767643928527832, 2.5866382122039795, 1.7760100364685059, 3.2526445388793945, 3.5857255458831787, 3.5383448600769043, 2.860339403152466, 2.8811466693878174, 3.256230354309082, 1.7942304611206055, 1.365021824836731, 2.9073193073272705, 3.4296252727508545, 3.0011932849884033, 2.008553981781006, 1.806180715560913, 2.7265353202819824, 2.8540539741516113, 3.4679274559020996, 2.327535629272461, 2.6652660369873047, 2.419222354888916, 1.7642792463302612, 2.451582193374634, 1.7254414558410645, 2.114943504333496, 1.781186580657959, 2.211029529571533, 2.719385862350464, 1.5628581047058105, 3.0332915782928467, 2.8618156909942627, 2.2945566177368164, 2.7361562252044678, 3.0826823711395264, 2.4744060039520264, 2.74845814704895, 2.533541679382324, 1.6822022199630737, 2.1876115798950195, 2.4029898643493652, 2.9106361865997314, 2.5871691703796387, 2.814837694168091, 2.6203339099884033, 2.1910715103149414, 2.8906469345092773, 2.9072673320770264, 2.307663917541504, 2.1303093433380127, 2.527859687805176, 1.7008253335952759, 2.10564923286438, 2.27968692779541, 2.284531593322754, 2.9296770095825195, 1.7555265426635742, 1.5704926252365112, 2.73297381401062, 2.4032161235809326, 2.8830273151397705, 3.232374906539917, 2.917322874069214, 1.9092283248901367, 2.797905445098877, 2.9846513271331787, 3.29280948638916, 1.8535833358764648, 2.416714668273926, 2.2865095138549805, 2.9811184406280518, 3.0803325176239014, 3.348313570022583, 2.370553731918335, 4.325446605682373, 3.5453004837036133, 2.5068390369415283, 2.2581989765167236, 0.24318456649780273, 0.22632186114788055, 0.25407320261001587, 0.1760147660970688, 0.20600798726081848, 0.22518499195575714, 0.1968996822834015, 0.24990390241146088, 0.2029116004705429, 0.25186002254486084, 0.2193511724472046, 0.21262067556381226, 0.17940181493759155, 0.21118636429309845, 0.21027614176273346, 0.17877449095249176, 0.21156780421733856, 0.14983057975769043, 0.16944599151611328, 0.21271350979804993, 0.2718622088432312, 0.249948650598526, 0.1541936844587326, 0.25409069657325745, 0.17814643681049347, 0.16493886709213257, 0.16471004486083984, 0.19673800468444824, 0.18619878590106964, 0.14836707711219788, 0.25855743885040283, 0.17395825684070587, 0.17819063365459442, 0.2952296733856201, 0.18409404158592224, 0.16257105767726898, 0.15962158143520355, 0.1885862648487091, 0.22160537540912628, 0.24270081520080566, 0.21164512634277344, 0.24122057855129242, 0.25836196541786194, 0.1855744570493698, 0.16316436231136322, 0.21769149601459503, 0.2168392688035965, 0.2716556787490845, 0.12708111107349396, 0.20709557831287384, 0.1953262835741043, 0.2429959774017334, 0.24224932491779327, 0.16943976283073425, 0.18856941163539886, 0.21064646542072296, 0.1829981505870819, 0.12461604923009872, 0.24370160698890686, 0.21966950595378876, 0.20807597041130066, 0.1603071242570877, 0.2305927276611328, 0.21471665799617767, 0.18595297634601593, 0.22506068646907806, 0.2521013021469116, 0.18293185532093048, 0.1948753446340561, 0.24117988348007202, 0.15817134082317352, 0.18783065676689148, 0.2013956755399704, 0.24111758172512054, 0.15457236766815186, 0.13764964044094086, 0.23778104782104492, 0.24929232895374298, 0.1899612694978714, 0.14832334220409393, 0.25635549426078796, 0.17944584786891937, 0.2210528552532196, 0.1926489770412445, 0.2089543640613556, 0.22308479249477386, 0.2067466676235199, 0.26414409279823303, 0.1902294158935547, 0.1544491946697235, 0.22743773460388184, 0.199098140001297, 0.17989091575145721, 0.18999865651130676, 0.17774493992328644, 0.2293100655078888, 0.23549386858940125, 0.17849956452846527, 0.21291740238666534, 0.2373868077993393, 0.2664157748222351, 0.26567092537879944, 0.2052662968635559, 0.17851696908473969, 0.22865329682826996, 0.15710404515266418, 0.21618326008319855, 0.17315557599067688, 0.23487673699855804, 0.15482942759990692, 0.15939940512180328, 0.17403052747249603, 0.24331240355968475, 0.236558735370636, 0.22717028856277466, 0.24295619130134583, 0.16683050990104675, 0.24881312251091003, 0.17428699135780334, 0.18173691630363464, 0.17691101133823395, 0.11579644680023193, 0.1248883381485939, 0.20462889969348907, 0.14364033937454224, 0.2033594846725464, 0.14394336938858032, 0.1850312203168869, 0.29383835196495056, 0.2197800725698471, 0.27552637457847595, 0.21541114151477814, 0.21518000960350037, 0.2206675261259079, 0.23326821625232697, 0.1868288815021515, 0.2035781443119049, 0.2555263340473175, 0.14170299470424652, 0.2322705239057541, 0.20510761439800262, 0.28212770819664, 0.23254378139972687, 0.18527285754680634, 0.19293048977851868, 0.20333713293075562, 0.20481669902801514, 0.234031081199646, 0.20397289097309113, 0.21654382348060608, 0.19568201899528503, 0.13627293705940247, 0.20403654873371124, 0.24002833664417267, 0.1636284589767456, 0.24988794326782227, 0.21378833055496216, 0.22383496165275574, 0.17280614376068115, 0.228962242603302, 0.14541897177696228, 0.2560204267501831, 0.1714094579219818, 0.219164177775383, 0.19269618391990662, 0.19403648376464844, 0.29390448331832886, 0.1255534142255783, 0.24520915746688843, 0.19454169273376465, 0.20762324333190918, 0.22582119703292847, 0.21264398097991943, 0.1475510597229004, 0.226556658744812, 0.1839134693145752, 0.2029191553592682, 0.18274028599262238, 0.23119086027145386, 0.19048544764518738, 0.17083464562892914, 0.22518520057201385, 0.201590895652771, 0.23627328872680664, 0.2820626497268677, 0.20433875918388367, 0.16708919405937195, 0.21969778835773468, 0.2609555721282959, 0.23025113344192505, 0.13579684495925903, 0.252439945936203, 0.21814820170402527, 0.14942224323749542, 0.25686854124069214, 0.25563639402389526, 0.2213861346244812, 0.13251808285713196, 0.24160902202129364, 0.19508880376815796, 0.15474490821361542, 0.23989470303058624, 0.14289160072803497, 0.2204418182373047, 0.21627803146839142, 0.22878295183181763, 0.2492147833108902, 0.162138894200325, 0.1660614013671875, 0.17747993767261505, 0.2208256721496582, 0.1614329069852829, 0.29528284072875977, 0.22449561953544617, 0.23411105573177338, 0.2513883113861084, 0.18978480994701385, 0.2116885483264923, 0.2053646594285965, 0.226455956697464, 0.22338920831680298, 0.256320059299469, 0.1999901980161667, 0.2027994841337204, 0.23787014186382294, 0.19727823138237, 0.22647728025913239, 0.14452846348285675, 0.16563403606414795, 0.224170982837677, 0.17865200340747833, 0.19481360912322998, 0.22287307679653168, 0.18644489347934723, 0.22594581544399261, 0.22258074581623077, 0.1740703135728836, 0.23781803250312805, 0.21215999126434326, 0.13110171258449554, 0.2021692991256714, 0.22348149120807648, 0.2111104130744934, 0.17013290524482727, 0.17718534171581268, 0.21398833394050598, 0.21843695640563965, 0.21402165293693542, 0.13578097522258759, 0.2674022316932678, 0.18887166678905487, 0.16825829446315765, 0.21751795709133148, 0.16188876330852509, 0.19796043634414673, 0.12852920591831207, 0.18893985450267792, 0.16421978175640106, 0.2032715380191803, 0.20661914348602295, 0.20108717679977417, 0.22743749618530273, 0.20009803771972656, 0.17165988683700562, 0.2270955741405487, 0.22165261209011078, 0.190936878323555, 0.18036098778247833, 0.11221776902675629, 0.19489727914333344, 0.1756427139043808, 0.17556796967983246, 0.22288651764392853, 0.1519165337085724, 0.2478250414133072, 0.16626712679862976, 0.21648968756198883, 0.1377042531967163, 0.23244528472423553, 0.1912239044904709, 0.2088339626789093, 0.1770831197500229, 0.2173071652650833, 0.20336423814296722, 0.2834089696407318, 0.2084483653306961, 0.11903665214776993, 0.204130619764328, 0.21530604362487793, 0.19437028467655182, 0.17709334194660187, 0.19034984707832336, 0.20651061832904816, 0.2078467458486557, 0.19448280334472656, 0.1634214222431183, 0.2447056919336319, 0.19037657976150513, 0.21431785821914673, 0.1718522608280182, 1.9880728721618652, 1.9596525430679321, 2.932629346847534, 1.4994131326675415, 2.1180531978607178, 1.7394992113113403, 1.249647855758667, 2.474412202835083, 1.897355556488037, 1.5411089658737183, 1.4762591123580933, 2.533907413482666, 1.2298165559768677, 2.948997974395752, 1.8963972330093384, 1.6382988691329956, 2.1595048904418945, 2.3625540733337402, 2.2704644203186035, 1.7411562204360962, 2.8805253505706787, 1.834311842918396, 2.477572441101074, 1.7149986028671265, 2.3427224159240723, 2.010232925415039, 2.1015751361846924, 1.811961054801941, 1.7193905115127563, 2.007582187652588, 1.3742176294326782, 1.4291247129440308, 1.5012575387954712, 1.943068504333496, 1.784455418586731, 1.1564892530441284, 3.265462875366211, 3.4697933197021484, 2.8966915607452393, 1.9230222702026367, 2.2979092597961426, 2.420623302459717, 2.6206157207489014, 2.5587844848632812, 2.2169435024261475, 1.971807837486267, 2.198209762573242, 2.0253448486328125, 1.7424688339233398, 1.4897361993789673, 1.8433265686035156, 2.09480619430542, 1.6820167303085327, 1.6331865787506104, 2.055528402328491, 1.5465011596679688, 2.13124680519104, 2.15165376663208, 3.082584857940674, 2.7071568965911865, 1.3261163234710693, 2.2978920936584473, 1.6586685180664062, 1.3272020816802979, 1.2682826519012451, 2.895371675491333, 2.106934070587158, 2.377701997756958, 1.9609670639038086, 1.3085732460021973, 1.625716209411621, 2.5870776176452637, 2.019538640975952, 2.2430801391601562, 1.869614839553833, 1.0875778198242188, 1.7313587665557861, 2.4012913703918457, 1.605350136756897, 1.5956698656082153, 1.352992057800293, 1.3694400787353516, 1.9341949224472046, 2.1252822875976562, 2.7930169105529785, 2.371762275695801, 1.2693099975585938, 1.5959430932998657, 1.4953052997589111, 1.2591110467910767, 3.4871373176574707, 2.0874757766723633, 1.3481191396713257, 2.180286407470703, 1.8137667179107666, 2.4750261306762695, 2.4384524822235107, 1.5307416915893555, 2.442690134048462, 0.9101971387863159, 1.4210119247436523, 1.5843136310577393, 2.619694232940674, 1.3698192834854126, 1.0852398872375488, 2.4184672832489014, 2.1869876384735107, 1.2643673419952393, 1.81783926486969, 1.2569953203201294, 1.95545494556427, 1.097653865814209, 2.1973226070404053, 1.3430970907211304, 2.8016133308410645, 2.485910177230835, 2.202322244644165, 1.3198041915893555, 2.455129384994507, 2.4938080310821533, 1.6091959476470947, 2.9571480751037598, 1.741685152053833, 2.462265968322754, 1.5975074768066406, 1.677947998046875, 1.847833514213562, 3.1631240844726562, 1.9511044025421143, 1.4998377561569214, 1.6809076070785522, 1.8188310861587524, 2.3968915939331055, 1.976135492324829, 2.4060072898864746, 1.5969979763031006, 2.2044365406036377, 2.901200532913208, 3.127042055130005, 2.1442975997924805, 1.8307987451553345, 1.1040751934051514, 1.2536535263061523, 2.4273619651794434, 2.25693416595459, 2.272808790206909, 1.6962498426437378, 2.192145347595215, 1.9077314138412476, 1.8078322410583496, 3.231157064437866, 1.4743402004241943, 1.4236208200454712, 1.2637996673583984, 1.4937946796417236, 1.7615106105804443, 1.5976864099502563, 1.4924697875976562, 2.030381202697754, 1.8845337629318237, 1.8542743921279907, 1.6471190452575684, 2.0365731716156006, 2.1871337890625, 1.6069930791854858, 1.8942865133285522, 1.4800459146499634, 1.456433892250061, 1.624558925628662, 1.2348172664642334, 2.156928062438965, 1.6460710763931274, 1.6091365814208984, 1.465941071510315, 1.1983517408370972, 1.7581514120101929, 2.711317777633667, 1.6951061487197876, 1.3114620447158813, 1.9786263704299927, 1.4603796005249023, 2.4181723594665527, 2.04850697517395, 2.0758144855499268, 3.271657943725586, 1.8998644351959229, 1.8060283660888672, 1.400357961654663, 1.2129507064819336, 1.9408422708511353, 1.6940041780471802, 1.9655414819717407, 1.7946767807006836, 2.40608811378479, 1.9781004190444946, 1.655411958694458, 3.2080955505371094, 1.9782379865646362, 2.3465373516082764, 1.7739521265029907, 1.7984237670898438, 1.9544130563735962, 2.0510215759277344, 1.4548619985580444, 1.7241010665893555, 2.094590902328491, 3.953946352005005, 2.082756519317627, 2.610931634902954, 1.7308095693588257, 1.8722012042999268, 2.5139827728271484, 1.6539640426635742, 1.9809379577636719, 0.9505172371864319, 1.6530159711837769, 1.5586700439453125, 1.6207022666931152, 2.2326879501342773, 1.495330810546875, 2.1381959915161133, 1.4152847528457642, 1.17576265335083, 1.9467562437057495, 2.0813534259796143, 2.351663827896118, 1.9767354726791382, 1.9468294382095337, 2.595508337020874, 2.9937963485717773, 1.9744638204574585, 2.37123966217041, 2.8366000652313232, 2.0994558334350586, 2.0626659393310547, 2.0102503299713135, 2.449366807937622, 1.864776849746704, 1.77144193649292, 2.4496755599975586, 2.829374313354492, 1.2249306440353394, 2.027432918548584, 1.9977816343307495, 1.525671362876892, 1.66802978515625, 2.1060566902160645, 1.7521013021469116, 2.9077706336975098, 2.698699951171875, 2.815864086151123, 1.7232322692871094, 2.1030521392822266, 1.8793537616729736, 2.0999789237976074, 2.7141852378845215, 1.4148461818695068, 2.0135140419006348, 2.7008190155029297, 3.263180732727051, 2.4407753944396973, 2.5254287719726562, 2.4710376262664795, 1.7790130376815796, 1.9665495157241821, 1.8919874429702759, 1.7477272748947144, 1.8194010257720947, 2.282151222229004, 3.0003268718719482, 1.8998043537139893, 2.181802988052368, 2.186044454574585, 2.0790600776672363, 1.3695108890533447, 2.283339500427246, 1.241574764251709, 2.5570356845855713, 1.9668083190917969, 2.38348126411438, 1.3128337860107422, 2.0125174522399902, 2.086167573928833, 2.2255423069000244, 1.6106047630310059, 1.7798737287521362, 1.5790085792541504, 1.5559895038604736, 1.981612205505371, 1.3345317840576172, 2.1921536922454834, 2.0447745323181152, 1.460854411125183, 1.086137294769287, 1.2516252994537354, 2.254429817199707, 1.7806987762451172, 2.5929646492004395, 1.9513658285140991, 2.6259753704071045, 38.024871826171875, 169.6204833984375, 339.15753173828125, 118.22772216796875, 158.94444274902344, 135.10479736328125, 309.4842224121094, 76.33370971679688, 136.4965362548828, 120.83140563964844, 464.0816345214844, 160.85015869140625, 260.49078369140625, 119.6508560180664, 107.98939514160156, 119.60595703125, 99.78751373291016, 126.68226623535156, 126.06620025634766, 67.85405731201172, 60.1837272644043, 97.93608856201172, 213.8777313232422, 142.13134765625, 45.844482421875, 115.88872528076172, 120.38530731201172, 91.92401885986328, 70.9876480102539, 35.520225524902344, 174.54150390625, 125.9417724609375, 138.73983764648438, 244.80413818359375, 40.767784118652344, 318.012451171875, 219.96702575683594, 48.8785400390625, 249.4165802001953, 120.68098449707031, 130.22015380859375, 260.01531982421875, 115.77445220947266, 56.92861557006836, 164.68255615234375, 104.37894439697266, 110.28582763671875, 190.79519653320312, 93.10823822021484, 33.4334716796875, 32.32535934448242, 107.37824249267578, 46.754638671875, 164.79742431640625, 129.27810668945312, 162.05284118652344, 146.76400756835938, 52.24554443359375, 83.55634307861328, 63.959228515625, 141.68194580078125, 142.22265625, 65.45162963867188, 119.97403717041016, 97.12923431396484, 72.53125, 138.59942626953125, 168.88792419433594, 90.39208984375, 165.47036743164062, 57.700042724609375, 143.45281982421875, 206.23220825195312, 67.93656158447266, 89.34464263916016, 225.0846405029297, 57.16268539428711, 301.2821350097656, 162.4500732421875, 90.07942962646484, 235.10302734375, 218.1087646484375, 105.3134765625, 145.75958251953125, 213.1644744873047, 97.4695816040039, 88.2313232421875, 47.095272064208984, 70.39921569824219, 127.23902130126953, 109.46109008789062, 121.7941665649414, 249.78372192382812, 197.3449249267578, 52.84716796875, 137.80352783203125, 52.201751708984375, 160.09922790527344, 180.7680206298828, 163.35272216796875, 322.7225036621094, 212.5487823486328, 123.52137756347656, 52.59599304199219, 300.7253723144531, 65.49053955078125, 451.0731506347656, 88.9488754272461, 170.48646545410156, 136.59503173828125, 227.85198974609375, 120.05420684814453, 168.98460388183594, 63.39761734008789, 27.623779296875, 172.586669921875, 165.22511291503906, 95.97384643554688, 46.576473236083984, 240.00613403320312, 76.3404541015625, 38.682289123535156, 285.5945739746094, 67.84809112548828, 86.0770263671875, 119.29706573486328, 141.88055419921875, 48.04448318481445, 214.43577575683594, 213.35382080078125, 188.54209899902344, 69.39099884033203, 80.53585052490234, 106.93035888671875, 374.2464904785156, 174.13734436035156, 131.09869384765625, 102.12263488769531, 142.9315948486328, 49.26613998413086, 249.7655792236328, 339.2882080078125, 26.715166091918945, 116.92241668701172, 157.6634521484375, 81.47415161132812, 204.8704833984375, 265.6091003417969, 40.85693359375, 139.29942321777344, 160.4066619873047, 70.88836669921875, 161.62510681152344, 135.8148193359375, 199.96051025390625, 47.50750732421875, 63.82215118408203, 48.325439453125, 44.93894958496094, 40.11024475097656, 142.60292053222656, 39.797607421875, 51.918758392333984, 259.57330322265625, 158.5326690673828, 60.90177536010742, 58.58277130126953, 141.093017578125, 181.144287109375, 71.71416473388672, 189.45562744140625, 302.9167785644531, 147.975341796875, 210.583740234375, 52.320281982421875, 79.220458984375, 34.28875732421875, 264.31488037109375, 69.32804870605469, 89.71341705322266, 45.31734848022461, 91.60527801513672, 205.41522216796875, 144.73538208007812, 211.939453125, 93.295166015625, 189.4735107421875, 73.16519165039062, 596.2730102539062, 70.50430297851562, 114.58600616455078, 77.005859375, 138.14048767089844, 127.30589294433594, 152.5319366455078, 141.86630249023438, 127.46986389160156, 212.0634765625, 88.4442138671875, 91.11711883544922, 364.7108459472656, 162.01177978515625, 169.0203857421875, 68.81420135498047, 93.88917541503906, 134.0008544921875, 195.5202178955078, 79.56341552734375, 111.00433349609375, 107.483642578125, 119.30138397216797, 89.60063934326172, 140.380859375, 190.1683349609375, 114.4901351928711, 115.789306640625, 259.2049865722656, 88.0572280883789, 333.1742248535156, 170.5664825439453, 147.8778839111328, 156.6153106689453, 122.69438934326172, 34.85137939453125, 112.70015716552734, 105.79413604736328, 210.40542602539062, 140.6718292236328, 144.45831298828125, 82.316162109375, 76.8748779296875, 66.02265167236328, 126.66944885253906, 46.9576416015625, 156.000732421875, 196.75335693359375, 262.9051818847656, 223.10194396972656, 111.5497055053711, 76.7479248046875, 45.52260971069336, 71.80874633789062, 128.68637084960938, 113.24085998535156, 146.5392303466797, 47.77790832519531, 38.35218048095703, 43.87493896484375, 51.40591812133789, 115.00666046142578, 243.55902099609375, 80.30389404296875, 122.07906341552734, 56.09649658203125, 178.0053253173828, 60.887611389160156, 151.83929443359375, 98.26280975341797, 229.0369110107422, 137.004150390625, 272.6657409667969, 164.3039093017578, 188.6605682373047, 113.4071273803711, 85.40435028076172, 53.594276428222656, 54.15784454345703, 189.914794921875, 254.6209259033203, 94.35421752929688, 103.68841552734375, 179.8470916748047, 64.7120361328125, 117.42716217041016, 103.45619201660156, 75.00552368164062, 246.88584899902344, 91.0589599609375, 115.71504974365234, 88.58625030517578, 36.946006774902344, 62.105281829833984, 133.97830200195312, 251.1358184814453, 47.717411041259766, 100.44232177734375, 49.144447326660156, 205.7099609375, 200.91476440429688, 101.36486053466797, 75.34776306152344, 39.905517578125, 83.10613250732422, 85.96125030517578, 134.89431762695312, 87.7578125, 89.5360107421875, 39.583160400390625, 273.82275390625, 224.1669158935547, 3.6567790508270264, 3.2186431884765625, 1.4005546569824219, 2.835158348083496, 1.8070833683013916, 2.723728656768799, 3.386371612548828, 1.955691933631897, 1.9553589820861816, 2.2425055503845215, 2.898977279663086, 3.6314480304718018, 2.8022897243499756, 1.689353346824646, 2.7507848739624023, 2.7550833225250244, 1.7462741136550903, 2.795454978942871, 3.106156587600708, 2.3954668045043945, 3.081934690475464, 3.9984006881713867, 3.1990208625793457, 2.587592124938965, 1.622939109802246, 2.856441020965576, 1.4133703708648682, 2.755350351333618, 2.9237565994262695, 2.6295852661132812, 2.664302349090576, 1.8109785318374634, 1.8816099166870117, 2.010057210922241, 3.474184989929199, 2.4424662590026855, 2.6927826404571533, 3.2033803462982178, 1.83537757396698, 1.8450901508331299, 1.3340920209884644, 3.1957757472991943, 2.5520007610321045, 2.192204475402832, 2.6856284141540527, 2.672961473464966, 2.750291109085083, 1.8941835165023804, 2.881373882293701, 1.7766977548599243, 2.0078725814819336, 3.41943359375, 2.816544771194458, 2.5062930583953857, 2.98044490814209, 1.4861478805541992, 3.4743545055389404, 2.7158355712890625, 1.9623137712478638, 2.3358590602874756, 3.970851421356201, 2.962982654571533, 2.724688768386841, 1.8365954160690308, 2.5934481620788574, 2.7709155082702637, 2.816981792449951, 1.9569625854492188, 2.192695379257202, 3.310612678527832, 1.980154037475586, 2.2531023025512695, 1.7202666997909546, 2.450312376022339, 3.566335439682007, 2.394608497619629, 2.527008533477783, 2.4541091918945312, 2.9618351459503174, 3.6102592945098877, 2.337974786758423, 1.5369443893432617, 2.1025917530059814, 2.506084442138672, 2.3151211738586426, 2.1137006282806396, 1.531794548034668, 2.3134853839874268, 1.9040344953536987, 3.2529308795928955, 2.2061269283294678, 1.9301319122314453, 1.8584342002868652, 2.233120918273926, 2.1633784770965576, 2.602783679962158, 3.13411545753479, 2.1650338172912598, 2.3659143447875977, 2.1982474327087402, 2.53023624420166, 3.388436794281006, 1.6650793552398682, 2.1241085529327393, 3.2280232906341553, 2.5511903762817383, 2.3596887588500977, 3.60546612739563, 1.475494384765625, 2.850435733795166, 3.6478631496429443, 2.553708076477051, 1.8964661359786987, 3.3977231979370117, 2.743025779724121, 1.6347079277038574, 2.371854782104492, 3.168968677520752, 2.0567140579223633, 1.9424058198928833, 2.198735237121582, 2.134221315383911, 4.059851169586182, 2.2926809787750244, 2.7714953422546387, 3.999518394470215, 2.1446831226348877, 1.720201015472412, 1.7096052169799805, 2.1256418228149414, 1.3682000637054443, 3.147711992263794, 2.1858904361724854, 1.946614146232605, 3.263714551925659, 2.4656152725219727, 2.1742849349975586, 2.180544853210449, 3.574591636657715, 3.0172836780548096, 2.1419994831085205, 2.582426071166992, 2.9459636211395264, 2.8673291206359863, 2.9332215785980225, 1.3562421798706055, 3.371363639831543, 1.3937301635742188, 2.3261032104492188, 1.6745290756225586, 2.901993989944458, 3.4722681045532227, 1.6318405866622925, 1.516224980354309, 2.664311408996582, 2.444883108139038, 2.2983970642089844, 2.60237979888916, 1.564908742904663, 2.6841704845428467, 1.5829987525939941, 1.8458009958267212, 3.7075047492980957, 3.33598256111145, 2.9256680011749268, 3.130662679672241, 3.5679893493652344, 3.5321648120880127, 2.860081672668457, 2.1838884353637695, 2.4837164878845215, 1.512323260307312, 3.489476203918457, 2.138627052307129, 2.7883214950561523, 2.0986318588256836, 2.8099586963653564, 3.5134057998657227, 1.650382399559021, 3.705578565597534, 3.5749244689941406, 2.36373233795166, 2.9260799884796143, 2.949542760848999, 2.333928346633911, 2.348719358444214, 2.790175676345825, 2.270202159881592, 2.192204475402832, 2.4579992294311523, 3.378237724304199, 1.9215104579925537, 2.758445978164673, 1.3319625854492188, 2.732154369354248, 2.5761706829071045, 2.734816551208496, 2.765368700027466, 2.6572887897491455, 1.795595407485962, 2.5125036239624023, 2.3198916912078857, 2.3030710220336914, 3.0253994464874268, 2.515336513519287, 3.5994081497192383, 2.5939955711364746, 3.411285400390625, 2.635138511657715, 3.0383641719818115, 2.1259241104125977, 2.661774158477783, 1.7117012739181519, 3.5908098220825195, 2.435530662536621, 1.788580298423767, 3.0055840015411377, 4.051217079162598, 2.5319509506225586, 3.139298677444458, 3.327946662902832, 1.717591404914856, 1.4405075311660767, 1.7807115316390991, 3.0964677333831787, 1.9953967332839966, 1.5067204236984253, 2.7136359214782715, 2.6990158557891846, 1.972481608390808, 1.6539074182510376, 1.9713706970214844, 3.464630603790283, 2.21748948097229, 2.160290241241455, 2.21663761138916, 2.247771978378296, 2.5762219429016113, 1.7453941106796265, 3.2898266315460205, 3.6607158184051514, 2.3237297534942627, 2.0620291233062744, 2.7028396129608154, 2.7494313716888428, 2.146160364151001, 1.5980545282363892, 3.372943878173828, 3.158778429031372, 2.347506284713745, 1.383137583732605, 2.332383155822754, 2.6066107749938965, 2.522937297821045, 1.9515905380249023, 2.6653575897216797, 3.528977632522583, 2.871652126312256, 2.051609992980957, 2.808455228805542, 1.5956581830978394, 1.9451360702514648, 2.7359650135040283, 3.225125551223755, 3.2130095958709717, 1.9315193891525269, 2.899289846420288, 1.2293845415115356, 2.668942451477051, 2.81942081451416, 2.120659828186035, 2.0845253467559814, 2.4017906188964844, 3.652353525161743, 0.9425764083862305, 2.551957845687866, 1.962525725364685, 2.3025662899017334, 1.8025857210159302, 2.746011257171631, 2.710768461227417, 1.512032389640808, 1.8802318572998047, 1.8328242301940918, 2.6698620319366455, 2.285647392272949, 3.752397298812866, 1.621937870979309, 2.928307056427002, 2.1715357303619385, 3.259591817855835, 2.8745927810668945, 2.656956672668457, 1.5048329830169678, 2.8273041248321533, 2.648759126663208, 3.0193779468536377, 3.4179065227508545, 1.6429604291915894, 2.8099701404571533, 0.14665544033050537, 0.19780147075653076, 0.17014095187187195, 0.12045741826295853, 0.17758403718471527, 0.20261158049106598, 0.2257581502199173, 0.19098792970180511, 0.20508357882499695, 0.16708305478096008, 0.19457457959651947, 0.2435891330242157, 0.2164408564567566, 0.21756121516227722, 0.23411516845226288, 0.17709369957447052, 0.20820169150829315, 0.20409034192562103, 0.1936958283185959, 0.17929603159427643, 0.15867739915847778, 0.2142350673675537, 0.2078014761209488, 0.19360791146755219, 0.21177098155021667, 0.20402662456035614, 0.2602991759777069, 0.19749900698661804, 0.14327198266983032, 0.21483691036701202, 0.18456602096557617, 0.20205004513263702, 0.1755509078502655, 0.1789017766714096, 0.22404460608959198, 0.22287195920944214, 0.18142519891262054, 0.18018116056919098, 0.19536395370960236, 0.2433885931968689, 0.21577830612659454, 0.20105914771556854, 0.17477525770664215, 0.24478213489055634, 0.22479473054409027, 0.1884768307209015, 0.21910898387432098, 0.25372278690338135, 0.17494013905525208, 0.24362526834011078, 0.19242946803569794, 0.2417457103729248, 0.2157358080148697, 0.16973777115345, 0.19866420328617096, 0.2576165199279785, 0.22283212840557098, 0.2723400890827179, 0.1553988754749298, 0.14983145892620087, 0.1825440526008606, 0.1866218000650406, 0.2186919003725052, 0.27348271012306213, 0.20703890919685364, 0.21638116240501404, 0.2073962390422821, 0.21019881963729858, 0.24418288469314575, 0.19984854757785797, 0.25625336170196533, 0.2522643208503723, 0.2302580624818802, 0.26637735962867737, 0.19822414219379425, 0.15556955337524414, 0.22094900906085968, 0.22383812069892883, 0.17682071030139923, 0.23107407987117767, 0.2259417325258255, 0.24714843928813934, 0.2239987701177597, 0.1821969896554947, 0.21354594826698303, 0.28253263235092163, 0.22720837593078613, 0.1342172473669052, 0.19671225547790527, 0.203175887465477, 0.23792621493339539, 0.12409724295139313, 0.22410617768764496, 0.22857311367988586, 0.14170587062835693, 0.1905345916748047, 0.15622392296791077, 0.2314515858888626, 0.2268557846546173, 0.2142118215560913, 0.18969783186912537, 0.17875340580940247, 0.27033093571662903, 0.17999684810638428, 0.21112574636936188, 0.1928299218416214, 0.1974114626646042, 0.19587881863117218, 0.2012198567390442, 0.19981548190116882, 0.1944381296634674, 0.22213050723075867, 0.16295062005519867, 0.20863784849643707, 0.25944238901138306, 0.207269549369812, 0.24995017051696777, 0.19228339195251465, 0.2849137783050537, 0.15785494446754456, 0.14677907526493073, 0.22562368214130402, 0.21326808631420135, 0.20712634921073914, 0.20521724224090576, 0.23661024868488312, 0.1804473102092743, 0.2254447340965271, 0.24818992614746094, 0.15752418339252472, 0.21137389540672302, 0.22731582820415497, 0.23746977746486664, 0.2521636486053467, 0.23877565562725067, 0.20307309925556183, 0.2877201735973358, 0.2121039479970932, 0.16630889475345612, 0.23740893602371216, 0.24934430420398712, 0.2590252161026001, 0.18276146054267883, 0.20464611053466797, 0.17956562340259552, 0.17073190212249756, 0.209669291973114, 0.223972350358963, 0.1809503138065338, 0.20214980840682983, 0.16951392590999603, 0.1809675246477127, 0.20738311111927032, 0.2225673943758011, 0.11918367445468903, 0.27246612310409546, 0.10780181735754013, 0.22860106825828552, 0.2837061285972595, 0.21505825221538544, 0.1575431376695633, 0.26586979627609253, 0.20342272520065308, 0.2500140964984894, 0.22075316309928894, 0.13649988174438477, 0.14256219565868378, 0.1296180635690689, 0.21672113239765167, 0.19224701821804047, 0.18984566628932953, 0.2356158345937729, 0.1846526712179184, 0.2048313021659851, 0.1548491269350052, 0.11345414072275162, 0.22978618741035461, 0.28654745221138, 0.14211156964302063, 0.11569682508707047, 0.24034327268600464, 0.2529293894767761, 0.1834067851305008, 0.1993648260831833, 0.20904220640659332, 0.15446247160434723, 0.18037086725234985, 0.21740874648094177, 0.16629329323768616, 0.17438378930091858, 0.17474140226840973, 0.188368558883667, 0.18538375198841095, 0.17917463183403015, 0.2571757137775421, 0.24088232219219208, 0.23046953976154327, 0.2529246509075165, 0.2207164764404297, 0.25086504220962524, 0.15971575677394867, 0.1628911942243576, 0.2727065682411194, 0.21178844571113586, 0.2072901427745819, 0.1591203212738037, 0.16099019348621368, 0.2972749173641205, 0.17569804191589355, 0.1784147471189499, 0.2887936234474182, 0.21591126918792725, 0.230635866522789, 0.21751895546913147, 0.14993374049663544, 0.18596965074539185, 0.22505328059196472, 0.17196126282215118, 0.1892576515674591, 0.25969797372817993, 0.22577941417694092, 0.181670144200325, 0.21182368695735931, 0.26771947741508484, 0.21712592244148254, 0.22339461743831635, 0.2231799215078354, 0.190901979804039, 0.24775822460651398, 0.21699200570583344, 0.21055109798908234, 0.2226269692182541, 0.19386553764343262, 0.2624623775482178, 0.20435428619384766, 0.1713346689939499, 0.2467222660779953, 0.22926577925682068, 0.1602698415517807, 0.19400222599506378, 0.16824109852313995, 0.20273633301258087, 0.21925555169582367, 0.22364643216133118, 0.2583865225315094, 0.2171948254108429, 0.2724628746509552, 0.2320287674665451, 0.19372355937957764, 0.2504548728466034, 0.28318050503730774, 0.23758506774902344, 0.18224845826625824, 0.16057613492012024, 0.16985443234443665, 0.2164512425661087, 0.18735244870185852, 0.22049735486507416, 0.1734275221824646, 0.19485245645046234, 0.18041633069515228, 0.13243228197097778, 0.26987263560295105, 0.17691874504089355, 0.22607570886611938, 0.14713187515735626, 0.1388145387172699, 0.21010057628154755, 0.19445109367370605, 0.17555107176303864, 0.25259581208229065, 0.20081260800361633, 0.16978740692138672, 0.22140608727931976, 0.20332923531532288, 0.19617168605327606, 0.2666795551776886, 0.25869056582450867, 0.1327006071805954, 0.20089206099510193, 0.18357451260089874, 0.20830762386322021, 0.2178298532962799, 0.1935308426618576, 0.23472952842712402, 0.2000974416732788, 0.21832746267318726, 0.2239011973142624, 0.2492002695798874, 0.17372018098831177, 0.16820643842220306, 0.20272281765937805, 0.19413016736507416, 0.20764735341072083, 0.24006514251232147, 0.27091240882873535, 0.1745660901069641, 0.16948477923870087, 0.3074619472026825, 0.23374485969543457, 2.3544490337371826, 2.1472268104553223, 2.124842405319214, 2.770815372467041, 2.288524627685547, 2.1510510444641113, 2.793827533721924, 1.4527370929718018, 2.20358943939209, 1.906505823135376, 2.1792194843292236, 2.1029067039489746, 2.4895424842834473, 1.6011654138565063, 1.439352035522461, 2.890002489089966, 1.9392427206039429, 2.0500147342681885, 1.624473214149475, 2.020217180252075, 1.879272699356079, 1.5661715269088745, 1.8403879404067993, 1.600464105606079, 1.3939484357833862, 2.3474786281585693, 1.3745774030685425, 1.695180892944336, 2.0775821208953857, 0.9541172385215759, 2.10269832611084, 1.671202301979065, 1.519545555114746, 2.051711082458496, 1.3681035041809082, 1.3572546243667603, 2.027848958969116, 1.6574779748916626, 1.7617782354354858, 1.4116086959838867, 2.188781499862671, 1.6655586957931519, 2.567655563354492, 1.9851824045181274, 2.0947704315185547, 1.6847742795944214, 1.4645025730133057, 2.08359694480896, 1.7296282052993774, 2.3095030784606934, 1.707739233970642, 2.1039884090423584, 1.982419729232788, 1.9420537948608398, 1.7448574304580688, 2.6906657218933105, 2.002729654312134, 1.8531379699707031, 2.1615500450134277, 2.3234825134277344, 1.3963617086410522, 1.6804757118225098, 1.7918099164962769, 1.734411597251892, 2.3283281326293945, 2.1399192810058594, 1.71584951877594, 2.5035951137542725, 1.7039763927459717, 2.0553274154663086, 1.585701584815979, 2.0916595458984375, 1.8915767669677734, 2.873917818069458, 1.2367016077041626, 1.7728878259658813, 1.9418773651123047, 2.2771835327148438, 2.14795184135437, 2.3503663539886475, 1.921054482460022, 2.2311666011810303, 3.1994106769561768, 3.0087525844573975, 2.104994773864746, 2.201371669769287, 1.7296254634857178, 1.5878571271896362, 2.383458137512207, 1.9895559549331665, 1.2663682699203491, 1.8468939065933228, 2.2479429244995117, 1.9580321311950684, 2.232585906982422, 2.1620540618896484, 2.5936436653137207, 2.137744665145874, 1.5939117670059204, 2.1624155044555664, 2.158247947692871, 0.9441137313842773, 1.6690380573272705, 2.115816593170166, 1.6408414840698242, 2.6704788208007812, 1.8555047512054443, 1.9268243312835693, 1.698452115058899, 2.3997769355773926, 2.2916312217712402, 1.8822300434112549, 2.2575159072875977, 1.3643447160720825, 1.352427363395691, 2.547374725341797, 1.9641145467758179, 1.8548409938812256, 0.9296396374702454, 1.391396164894104, 1.9787273406982422, 2.578544855117798, 1.3222728967666626, 1.303679347038269, 1.9700933694839478, 2.1594901084899902, 1.074194073677063, 1.6576563119888306, 2.27286958694458, 1.4040353298187256, 2.652362108230591, 3.0274205207824707, 3.02451491355896, 1.990368127822876, 1.8380024433135986, 2.1104583740234375, 2.6888084411621094, 2.3993637561798096, 2.539618968963623, 2.492152690887451, 1.9002457857131958, 1.9454759359359741, 1.4843990802764893, 1.9646438360214233, 1.7408937215805054, 1.3262734413146973, 1.7460405826568604, 2.9271187782287598, 1.70919668674469, 1.4567301273345947, 2.5666937828063965, 2.312246084213257, 1.865409255027771, 2.2772233486175537, 2.7742137908935547, 1.5521055459976196, 1.6592979431152344, 1.9308626651763916, 1.8381105661392212, 2.090273857116699, 2.3036105632781982, 2.023735284805298, 2.239290475845337, 2.007734537124634, 2.133104085922241, 2.727036714553833, 2.4391322135925293, 1.4311290979385376, 1.7579189538955688, 1.2524163722991943, 1.6365587711334229, 2.199176549911499, 2.0355887413024902, 2.519007921218872, 2.0096054077148438, 1.1954728364944458, 2.4044597148895264, 2.719151020050049, 2.5141797065734863, 2.4913625717163086, 2.2719926834106445, 2.3249456882476807, 2.465087890625, 2.679999589920044, 1.1812191009521484, 2.1032283306121826, 2.7429473400115967, 2.46632719039917, 1.4280624389648438, 2.5834922790527344, 2.489659547805786, 1.8187522888183594, 2.803792953491211, 2.483474016189575, 1.6357828378677368, 2.5381882190704346, 2.5707085132598877, 2.168043375015259, 1.0658847093582153, 0.9541531801223755, 2.3155837059020996, 1.5989567041397095, 1.383477807044983, 1.604034662246704, 1.4692022800445557, 1.2882992029190063, 2.2884631156921387, 1.6010842323303223, 2.4051849842071533, 1.4500855207443237, 1.3132352828979492, 1.336609125137329, 1.8987435102462769, 2.3294408321380615, 2.0953259468078613, 1.3749626874923706, 2.640939474105835, 1.89669668674469, 1.8180347681045532, 1.3160161972045898, 1.2884712219238281, 1.3916412591934204, 1.4495937824249268, 1.9140466451644897, 2.0532305240631104, 2.32287859916687, 2.445885181427002, 1.9571717977523804, 1.369425654411316, 1.864849328994751, 1.8230133056640625, 3.7359025478363037, 1.6791329383850098, 1.3105562925338745, 1.671708583831787, 1.8488082885742188, 2.6801669597625732, 1.051080346107483, 2.6472954750061035, 2.006075859069824, 2.244645118713379, 1.7956571578979492, 2.08547306060791, 1.8206138610839844, 2.0980303287506104, 2.845288038253784, 1.7951568365097046, 1.5145988464355469, 2.3857600688934326, 3.024374008178711, 1.9848546981811523, 2.3563756942749023, 1.6429351568222046, 2.710031747817993, 2.3423266410827637, 1.5975157022476196, 2.528663158416748, 1.4603525400161743, 1.946242332458496, 2.302137613296509, 2.331690549850464, 2.4569592475891113, 1.2915700674057007, 2.3340516090393066, 1.816846251487732, 1.7401260137557983, 3.580900192260742, 1.2806237936019897, 1.8649063110351562, 1.5649694204330444, 1.7030800580978394, 1.7860113382339478, 1.7938807010650635, 1.7434862852096558, 2.0049149990081787, 1.7519785165786743, 1.350904107093811, 2.3229401111602783, 2.5677459239959717, 1.4736700057983398, 2.0815510749816895, 2.2340188026428223, 2.4168710708618164, 1.458901047706604, 2.094115972518921, 2.394132137298584, 1.4600368738174438, 3.2317070960998535, 1.7010929584503174, 2.7465732097625732, 1.3108854293823242, 1.2805101871490479, 2.536242961883545, 2.1175060272216797, 1.1727161407470703, 1.645477294921875, 1.9781169891357422, 1.5463110208511353, 1.6152453422546387, 2.0397427082061768, 84.83263397216797, 40.66754150390625, 187.9462432861328, 202.3820343017578, 100.3509521484375, 204.0630645751953, 315.34832763671875, 301.5462951660156, 232.5572967529297, 254.55340576171875, 132.16293334960938, 219.22576904296875, 158.74346923828125, 46.423919677734375, 117.810302734375, 209.75804138183594, 58.3006591796875, 252.9120330810547, 203.0146026611328, 47.38105010986328, 123.49710845947266, 260.54345703125, 158.1327362060547, 133.6379852294922, 79.24988555908203, 249.13299560546875, 219.0701141357422, 58.249847412109375, 115.3660888671875, 209.33428955078125, 86.3358154296875, 313.8141784667969, 112.17694091796875, 105.58954620361328, 151.45469665527344, 30.0889892578125, 138.39068603515625, 188.96902465820312, 162.90240478515625, 97.43340301513672, 43.259925842285156, 57.861053466796875, 206.24514770507812, 278.60650634765625, 44.611507415771484, 141.54864501953125, 51.49725341796875, 529.4810791015625, 263.67193603515625, 122.66320037841797, 209.51104736328125, 32.01645278930664, 159.037353515625, 65.701416015625, 138.18438720703125, 95.609375, 43.7034797668457, 95.95211029052734, 97.3616714477539, 197.91712951660156, 217.927734375, 139.1874237060547, 203.6176300048828, 110.50425720214844, 90.17491912841797, 139.7489013671875, 239.5556182861328, 170.28721618652344, 108.01979064941406, 55.65444564819336, 176.2274932861328, 218.10354614257812, 259.26885986328125, 181.28952026367188, 197.4225616455078, 89.22119140625, 83.251953125, 116.20708465576172, 142.7928924560547, 56.587646484375, 227.13246154785156, 71.061279296875, 196.4520263671875, 187.02171325683594, 122.31809997558594, 187.30441284179688, 250.7266387939453, 42.271053314208984, 66.80020141601562, 92.77171325683594, 34.328617095947266, 36.31732177734375, 101.2367935180664, 279.6499938964844, 202.21702575683594, 162.35955810546875, 188.55067443847656, 110.3470458984375, 107.84394073486328, 131.0409698486328, 124.95802307128906, 144.6793975830078, 515.0382080078125, 234.0419921875, 144.77288818359375, 255.69300842285156, 101.51214599609375, 78.94581604003906, 195.08328247070312, 224.15847778320312, 198.3819122314453, 178.01283264160156, 123.63048553466797, 93.7957763671875, 115.1488037109375, 133.82675170898438, 143.5155029296875, 114.02794647216797, 336.6805419921875, 368.925537109375, 40.55466842651367, 103.62357330322266, 55.008056640625, 88.120849609375, 216.35986328125, 133.0956573486328, 187.819091796875, 54.46112060546875, 246.1885528564453, 131.26312255859375, 233.13323974609375, 158.47848510742188, 169.7042999267578, 167.01522827148438, 102.27294921875, 39.09759521484375, 48.53281021118164, 186.96554565429688, 62.629276275634766, 180.6830291748047, 145.2322998046875, 405.0746765136719, 303.330810546875, 344.5581970214844, 182.7223358154297, 37.4613037109375, 206.28759765625, 208.07550048828125, 226.37509155273438, 182.7743377685547, 252.0185546875, 75.0189208984375, 45.45111083984375, 127.75408172607422, 77.8440933227539, 73.08550262451172, 30.604442596435547, 58.02155303955078, 69.38990783691406, 159.406982421875, 141.69525146484375, 221.31585693359375, 52.046600341796875, 174.0264434814453, 55.55837631225586, 113.624755859375, 85.7980728149414, 44.856258392333984, 64.12264251708984, 347.34930419921875, 122.22714233398438, 114.205322265625, 102.19493865966797, 77.51919555664062, 72.5904541015625, 29.384305953979492, 380.15771484375, 36.186859130859375, 50.38861083984375, 206.5640411376953, 76.63916015625, 69.15316009521484, 117.45663452148438, 37.90826416015625, 227.702880859375, 249.40692138671875, 151.46099853515625, 100.42252349853516, 141.742919921875, 150.3020782470703, 123.9372329711914, 161.90191650390625, 151.07772827148438, 84.60503387451172, 92.98628997802734, 51.90970230102539, 189.64035034179688, 88.04984283447266, 57.20521926879883, 35.57754135131836, 72.15130615234375, 68.36930847167969, 76.9515609741211, 142.43310546875, 95.2596435546875, 41.735164642333984, 238.2349395751953, 116.90691375732422, 142.662841796875, 173.4811553955078, 161.99473571777344, 251.0778045654297, 184.8375701904297, 86.5804214477539, 144.86151123046875, 185.3485870361328, 330.65875244140625, 285.59893798828125, 173.9793701171875, 87.10589599609375, 194.79345703125, 55.174720764160156, 76.68577575683594, 42.14504623413086, 114.2946548461914, 37.003055572509766, 80.26361083984375, 188.41558837890625, 64.26852416992188, 252.18240356445312, 216.83108520507812, 212.32293701171875, 109.77919006347656, 126.20111083984375, 201.2554473876953, 264.7679443359375, 140.18870544433594, 171.2850341796875, 162.0262908935547, 232.7675323486328, 140.361328125, 185.6839141845703, 71.69772338867188, 46.99372100830078, 66.32353973388672, 208.7333526611328, 139.1880645751953, 182.1560821533203, 123.44609832763672, 61.0654296875, 101.82621002197266, 85.09386444091797, 210.8265380859375, 86.26954650878906, 69.91497802734375, 210.20127868652344, 44.540828704833984, 169.41722106933594, 220.47479248046875, 97.4173812866211, 242.0535888671875, 40.45433044433594, 169.9088592529297, 77.91302490234375, 89.6522216796875, 155.8268585205078, 134.63543701171875, 140.59530639648438, 235.66030883789062, 180.9886932373047, 363.9823303222656, 93.78006744384766, 62.58496856689453, 50.53261947631836, 392.2462463378906, 258.7947998046875, 269.9342041015625, 36.190223693847656, 219.61143493652344, 55.16595458984375, 69.82839965820312, 203.5720672607422, 218.64697265625, 40.15017318725586, 255.9839630126953, 96.982421875, 341.91650390625, 253.6605987548828, 120.58558654785156, 112.07691955566406, 207.59043884277344, 34.86627197265625, 219.90066528320312, 189.5352325439453, 127.23493957519531, 189.06878662109375, 38.67987060546875, 51.166629791259766, 190.24574279785156, 139.9962921142578, 1.3854421377182007, 3.0811188220977783, 2.6067607402801514, 1.9108432531356812, 2.3532207012176514, 2.306307077407837, 1.9039009809494019, 2.641833543777466, 2.5897674560546875, 1.9969147443771362, 2.1602866649627686, 1.7733891010284424, 3.300893545150757, 3.3636651039123535, 1.337723970413208, 2.4701201915740967, 1.5889147520065308, 3.3930599689483643, 2.6799702644348145, 1.598414421081543, 2.2466676235198975, 2.6477038860321045, 2.3460566997528076, 3.072329044342041, 2.3869659900665283, 2.517693042755127, 2.548470973968506, 2.635615825653076, 1.9281530380249023, 2.727353572845459, 2.071078300476074, 2.6774401664733887, 3.44975209236145, 2.2402069568634033, 1.6903327703475952, 2.4354841709136963, 2.2895631790161133, 2.2343626022338867, 2.429718494415283, 1.8480334281921387, 1.9253170490264893, 1.4251574277877808, 3.306452751159668, 2.518631935119629, 2.3239247798919678, 1.6035033464431763, 3.2486953735351562, 2.3841164112091064, 3.5421645641326904, 2.282160758972168, 2.3298027515411377, 1.8892279863357544, 2.229825019836426, 2.1679768562316895, 2.428866147994995, 1.7316848039627075, 3.1321499347686768, 2.6072967052459717, 1.755239486694336, 2.373703956604004, 1.5011348724365234, 2.517517566680908, 2.747894287109375, 2.848006010055542, 3.423792839050293, 2.0327348709106445, 1.7996147871017456, 2.764117479324341, 2.694066047668457, 3.49039363861084, 2.093419075012207, 3.118408203125, 2.3172731399536133, 2.885648012161255, 2.476506233215332, 1.4717882871627808, 2.6990575790405273, 2.4786810874938965, 1.686055064201355, 3.6881954669952393, 1.4728745222091675, 1.8457882404327393, 2.983919620513916, 2.5664050579071045, 2.344740867614746, 1.6498879194259644, 2.13507342338562, 1.7613457441329956, 3.521834135055542, 2.4469194412231445, 1.7691411972045898, 3.265261650085449, 2.1504948139190674, 1.6174812316894531, 2.2401533126831055, 3.491241931915283, 1.7505956888198853, 2.844393253326416, 1.9601165056228638, 2.162482261657715, 3.073134183883667, 2.9119484424591064, 2.3738982677459717, 2.6716582775115967, 2.63601016998291, 2.72794508934021, 2.9665942192077637, 1.03899085521698, 3.5775957107543945, 2.7020788192749023, 4.383613109588623, 1.8399895429611206, 2.5835907459259033, 1.8313922882080078, 3.646125316619873, 1.6049842834472656, 2.1312620639801025, 2.0836174488067627, 2.5018362998962402, 1.7956218719482422, 3.2892961502075195, 2.04885196685791, 1.3528013229370117, 2.361631155014038, 2.543276786804199, 2.2819910049438477, 1.9806450605392456, 2.356532335281372, 2.9745569229125977, 4.086098670959473, 2.242037773132324, 2.497286319732666, 1.7794159650802612, 1.7521342039108276, 3.182220458984375, 2.187161445617676, 3.2262990474700928, 2.2938404083251953, 3.099322557449341, 2.4503047466278076, 1.8873074054718018, 3.0692055225372314, 1.7195827960968018, 1.610005497932434, 2.507831335067749, 1.9877538681030273, 1.5689430236816406, 3.420535087585449, 2.4616920948028564, 3.3255715370178223, 2.712895393371582, 2.1981210708618164, 2.579730272293091, 3.0856335163116455, 2.8080554008483887, 2.8192169666290283, 2.4585933685302734, 2.136815071105957, 1.9489275217056274, 2.435565710067749, 2.774876594543457, 2.563906192779541, 2.1499228477478027, 1.4332647323608398, 3.257674217224121, 1.56861412525177, 1.7400678396224976, 2.828275680541992, 3.4105749130249023, 1.5226409435272217, 2.35742449760437, 3.5250511169433594, 3.323115110397339, 2.6818902492523193, 3.291638135910034, 1.7281644344329834, 2.604144334793091, 3.6547536849975586, 1.4337624311447144, 4.266019344329834, 2.898533344268799, 3.1352179050445557, 3.1250107288360596, 1.7942637205123901, 1.8696928024291992, 2.4323885440826416, 1.3392802476882935, 2.596423387527466, 3.440842866897583, 2.662930488586426, 1.801971673965454, 3.0258402824401855, 2.5456886291503906, 2.5360422134399414, 1.7809966802597046, 3.4423372745513916, 2.9312846660614014, 3.8040153980255127, 2.876154661178589, 1.8701756000518799, 2.6835012435913086, 2.3209619522094727, 2.9891252517700195, 2.137925624847412, 2.406590461730957, 1.4793238639831543, 2.103618621826172, 3.624403953552246, 2.301703453063965, 2.5508639812469482, 2.6081151962280273, 2.614180326461792, 2.931535005569458, 1.5033310651779175, 2.4712095260620117, 2.778949737548828, 1.6839475631713867, 3.1455624103546143, 3.6856298446655273, 1.8682656288146973, 3.5796597003936768, 2.002232551574707, 1.79280424118042, 1.6336338520050049, 2.1278746128082275, 2.814654588699341, 3.4383955001831055, 3.1550586223602295, 3.7753007411956787, 3.3152787685394287, 1.8998955488204956, 3.346210241317749, 2.686246871948242, 3.4550304412841797, 3.605557680130005, 2.215528726577759, 3.1189510822296143, 3.496959686279297, 2.808781623840332, 2.9186320304870605, 2.3404626846313477, 3.4977006912231445, 1.9563274383544922, 3.9289162158966064, 3.3098325729370117, 3.092625617980957, 2.0957159996032715, 3.0839340686798096, 2.8363847732543945, 2.2173423767089844, 3.266932487487793, 1.9662140607833862, 1.9353017807006836, 2.7972569465637207, 2.0505666732788086, 2.8122355937957764, 2.2777607440948486, 2.898638963699341, 2.9684648513793945, 1.4952720403671265, 3.8702821731567383, 2.971644639968872, 1.4188567399978638, 3.6536247730255127, 2.3616185188293457, 1.9023560285568237, 1.4930449724197388, 3.656759023666382, 3.1952202320098877, 2.7421116828918457, 3.10074520111084, 2.9881036281585693, 3.0947489738464355, 2.7030043601989746, 2.372725486755371, 2.781097888946533, 1.9358452558517456, 2.3578779697418213, 1.851038932800293, 1.5923566818237305, 2.3814029693603516, 2.0878851413726807, 1.6131631135940552, 2.2065045833587646, 2.768927574157715, 2.1898889541625977, 3.0581626892089844, 1.9736512899398804, 2.1618309020996094, 2.6194872856140137, 2.6815905570983887, 2.6617462635040283, 1.5977190732955933, 1.8143911361694336, 2.0624094009399414, 4.088671684265137, 2.480710506439209, 2.1724581718444824, 2.576092481613159, 1.8356993198394775, 0.17394855618476868, 0.1464548110961914, 0.28154534101486206, 0.16652637720108032, 0.2920427918434143, 0.2981536388397217, 0.2169061005115509, 0.2077191174030304, 0.20042064785957336, 0.22476118803024292, 0.1980707198381424, 0.21562987565994263, 0.20841681957244873, 0.23158809542655945, 0.14221687614917755, 0.19541560113430023, 0.18047641217708588, 0.22907483577728271, 0.2456870824098587, 0.20295673608779907, 0.21009017527103424, 0.17286913096904755, 0.19755294919013977, 0.15474289655685425, 0.22566737234592438, 0.3311547636985779, 0.20113269984722137, 0.18206386268138885, 0.17077060043811798, 0.2527761161327362, 0.22254207730293274, 0.18037064373493195, 0.28567788004875183, 0.11880684643983841, 0.21780560910701752, 0.180032417178154, 0.20677411556243896, 0.20055554807186127, 0.2526017725467682, 0.21702592074871063, 0.19811208546161652, 0.27649161219596863, 0.17101478576660156, 0.2172168642282486, 0.18890516459941864, 0.20921607315540314, 0.1795049011707306, 0.16084454953670502, 0.2574102282524109, 0.18551328778266907, 0.20359785854816437, 0.20491944253444672, 0.18352119624614716, 0.19008731842041016, 0.19530345499515533, 0.19968055188655853, 0.15589918196201324, 0.20389369130134583, 0.17529597878456116, 0.24555201828479767, 0.2140570729970932, 0.23129825294017792, 0.23113776743412018, 0.16477391123771667, 0.2314261794090271, 0.26303595304489136, 0.22962859272956848, 0.23525190353393555, 0.2734459638595581, 0.17921699583530426, 0.20828039944171906, 0.21646106243133545, 0.15048623085021973, 0.14451751112937927, 0.12061290442943573, 0.24112224578857422, 0.19396646320819855, 0.1735701858997345, 0.2680926024913788, 0.20371389389038086, 0.19842174649238586, 0.2446948140859604, 0.26190075278282166, 0.2091647982597351, 0.24445563554763794, 0.15348969399929047, 0.1783156394958496, 0.2119734287261963, 0.1758829802274704, 0.08685237914323807, 0.26888811588287354, 0.1711852252483368, 0.19415874779224396, 0.18552672863006592, 0.22532537579536438, 0.20714171230793, 0.19848355650901794, 0.26063528656959534, 0.2561746835708618, 0.2301689237356186, 0.19674193859100342, 0.15806080400943756, 0.24459770321846008, 0.17470300197601318, 0.2775901257991791, 0.17499923706054688, 0.2077290266752243, 0.2400246411561966, 0.19958573579788208, 0.2350679486989975, 0.230634868144989, 0.2760636508464813, 0.23266667127609253, 0.236270934343338, 0.20851804316043854, 0.2262556403875351, 0.19413335621356964, 0.21266396343708038, 0.20467324554920197, 0.23477858304977417, 0.24708545207977295, 0.24997448921203613, 0.20798556506633759, 0.2690856158733368, 0.2356928586959839, 0.2487410306930542, 0.2780245244503021, 0.22122111916542053, 0.1965969055891037, 0.18183016777038574, 0.21765853464603424, 0.23167483508586884, 0.21916277706623077, 0.18976302444934845, 0.1253344714641571, 0.20841677486896515, 0.2490396797657013, 0.22226911783218384, 0.11376279592514038, 0.21096324920654297, 0.17133094370365143, 0.20360176265239716, 0.16266761720180511, 0.22147716581821442, 0.2410689890384674, 0.1923656016588211, 0.21383841335773468, 0.19975818693637848, 0.16632157564163208, 0.14592061936855316, 0.2034403532743454, 0.22037486732006073, 0.21708907186985016, 0.2016357034444809, 0.2654262185096741, 0.17350244522094727, 0.22199729084968567, 0.1932157725095749, 0.22442029416561127, 0.22757361829280853, 0.21193712949752808, 0.1618853658437729, 0.18639414012432098, 0.2660057246685028, 0.2596096396446228, 0.17343099415302277, 0.20106437802314758, 0.22673527896404266, 0.13360315561294556, 0.2086859494447708, 0.18632864952087402, 0.22265130281448364, 0.19602015614509583, 0.24634875357151031, 0.11346253752708435, 0.14287590980529785, 0.20928643643856049, 0.18794624507427216, 0.18140056729316711, 0.2325306236743927, 0.24572470784187317, 0.21900580823421478, 0.20268893241882324, 0.20275592803955078, 0.19929830729961395, 0.15035948157310486, 0.21135945618152618, 0.21246562898159027, 0.24098795652389526, 0.1950286626815796, 0.17616911232471466, 0.1530051827430725, 0.15584725141525269, 0.2559145390987396, 0.20769698917865753, 0.18113544583320618, 0.25583288073539734, 0.17231948673725128, 0.2620869278907776, 0.24594634771347046, 0.2011379599571228, 0.25339218974113464, 0.22523750364780426, 0.22969354689121246, 0.17933900654315948, 0.13921602070331573, 0.17995326220989227, 0.3169148564338684, 0.18987542390823364, 0.21307988464832306, 0.23229524493217468, 0.18138021230697632, 0.251888245344162, 0.18938155472278595, 0.17210502922534943, 0.210662841796875, 0.23753349483013153, 0.1181374117732048, 0.1954268217086792, 0.20042617619037628, 0.18085332214832306, 0.19565778970718384, 0.18076902627944946, 0.22698818147182465, 0.2100973129272461, 0.19086891412734985, 0.19410096108913422, 0.24292273819446564, 0.21208085119724274, 0.17179656028747559, 0.267019122838974, 0.20643700659275055, 0.22245025634765625, 0.2144748568534851, 0.17189010977745056, 0.17453281581401825, 0.2204282134771347, 0.20557670295238495, 0.16916011273860931, 0.16940295696258545, 0.21504420042037964, 0.1881909966468811, 0.15776269137859344, 0.2208307534456253, 0.2625751793384552, 0.2005932629108429, 0.21572162210941315, 0.22631171345710754, 0.176441952586174, 0.24116434156894684, 0.19001486897468567, 0.23140692710876465, 0.17288394272327423, 0.15750689804553986, 0.17980928719043732, 0.20064806938171387, 0.15831805765628815, 0.1668562889099121, 0.2598028779029846, 0.2171047180891037, 0.23606376349925995, 0.21172255277633667, 0.2318381816148758, 0.21245916187763214, 0.12173688411712646, 0.2982754707336426, 0.26793819665908813, 0.1707819402217865, 0.18269255757331848, 0.216090127825737, 0.23496267199516296, 0.1820545494556427, 0.17534556984901428, 0.2929460406303406, 0.2571529150009155, 0.16596923768520355, 0.20719119906425476, 0.22898223996162415, 0.1854141801595688, 0.22940704226493835, 0.19050168991088867, 0.18234314024448395, 0.19486631453037262, 0.24470427632331848, 0.20013263821601868, 0.23236970603466034, 0.15743979811668396, 0.16113683581352234, 0.22625136375427246, 0.1860811561346054, 0.17721134424209595, 0.19769637286663055, 0.19305875897407532, 0.20220157504081726, 0.16004414856433868, 0.19516301155090332, 0.20251066982746124, 0.18374083936214447, 0.2396353930234909, 0.1753825694322586, 2.270801544189453, 2.237281084060669, 1.5835189819335938, 1.3665269613265991, 2.956136703491211, 2.12785267829895, 2.851517915725708, 2.622514486312866, 1.7465165853500366, 1.6621729135513306, 1.5083048343658447, 1.1335238218307495, 1.4514967203140259, 1.21390700340271, 2.2488625049591064, 1.9259047508239746, 2.744631290435791, 2.3905081748962402, 1.2065753936767578, 3.096177577972412, 2.072826385498047, 1.9499775171279907, 3.114389181137085, 1.7485147714614868, 1.7320448160171509, 2.1720852851867676, 2.1474032402038574, 1.3033034801483154, 2.5420870780944824, 1.2620441913604736, 1.9559730291366577, 1.992238998413086, 3.253398895263672, 2.4256863594055176, 2.0080816745758057, 2.770153760910034, 1.994588851928711, 1.4966964721679688, 1.7458328008651733, 2.5809459686279297, 1.7881749868392944, 1.4726812839508057, 2.0591230392456055, 1.7371326684951782, 2.1034328937530518, 1.9621323347091675, 1.7101320028305054, 1.701438307762146, 2.0974907875061035, 2.618119955062866, 1.5863995552062988, 1.8023496866226196, 2.5337300300598145, 2.331653594970703, 2.4051034450531006, 2.7352936267852783, 2.217529058456421, 2.648745059967041, 1.1607694625854492, 2.2549819946289062, 2.405465841293335, 2.703042507171631, 1.7559788227081299, 2.031677007675171, 1.7142301797866821, 1.9785314798355103, 1.9482977390289307, 1.6300230026245117, 1.7889703512191772, 2.0802383422851562, 2.3749208450317383, 2.804056406021118, 2.4581918716430664, 1.4819048643112183, 1.673844814300537, 1.7212259769439697, 2.771611213684082, 1.840545892715454, 1.5742098093032837, 1.907407283782959, 1.9945201873779297, 2.725262403488159, 1.4204113483428955, 2.015815019607544, 1.5349575281143188, 1.7842075824737549, 1.5408462285995483, 1.3901150226593018, 2.717989444732666, 2.35852313041687, 1.9660084247589111, 2.013486862182617, 2.0064444541931152, 2.0822043418884277, 2.354186534881592, 2.859004497528076, 2.6329808235168457, 0.9310325980186462, 2.3444414138793945, 2.6744284629821777, 2.564617872238159, 2.3987207412719727, 1.5431289672851562, 2.569354295730591, 2.742816686630249, 1.8025264739990234, 2.4408717155456543, 2.3689558506011963, 3.3438987731933594, 2.588853120803833, 2.439917802810669, 2.396509885787964, 2.0919885635375977, 1.824002981185913, 2.135087490081787, 1.464996337890625, 2.419060707092285, 1.7578991651535034, 2.154897928237915, 2.2048120498657227, 2.156482696533203, 2.5706076622009277, 1.823758840560913, 2.243720054626465, 1.687952995300293, 1.8964512348175049, 2.409923553466797, 2.041741371154785, 1.62150239944458, 2.9062469005584717, 1.731509804725647, 1.9726165533065796, 1.7515769004821777, 2.3129756450653076, 2.572138547897339, 1.998975157737732, 1.7781976461410522, 2.1491875648498535, 1.401968002319336, 1.6166568994522095, 2.2162227630615234, 1.9339860677719116, 2.6115875244140625, 2.0994856357574463, 1.6425083875656128, 1.5058343410491943, 1.4946950674057007, 1.9346084594726562, 1.8655509948730469, 2.6929543018341064, 1.6605944633483887, 2.043382406234741, 1.7406471967697144, 1.4363819360733032, 3.128143310546875, 1.1043320894241333, 1.888771653175354, 2.9923393726348877, 1.8141359090805054, 2.268639087677002, 2.5071001052856445, 1.298417329788208, 1.820113182067871, 2.4657797813415527, 1.5445940494537354, 1.9104838371276855, 1.6803661584854126, 1.8811430931091309, 2.06551456451416, 1.49163818359375, 1.8077272176742554, 2.7326672077178955, 2.5304806232452393, 2.743975877761841, 1.990316390991211, 1.494745135307312, 1.9355639219284058, 2.0104198455810547, 1.4283332824707031, 2.609607458114624, 1.6366474628448486, 1.5849770307540894, 2.177011728286743, 2.9415764808654785, 2.155458688735962, 1.8688395023345947, 1.499593734741211, 2.6242570877075195, 2.2102530002593994, 2.2151405811309814, 2.794992685317993, 1.433868646621704, 2.0545639991760254, 2.150479316711426, 1.8705321550369263, 2.7220709323883057, 2.6779778003692627, 1.7319300174713135, 2.2099103927612305, 1.7693849802017212, 2.0393800735473633, 2.240673542022705, 1.8878358602523804, 3.438049793243408, 1.58099365234375, 1.9467159509658813, 1.9396870136260986, 2.5002963542938232, 1.5419098138809204, 1.8320786952972412, 2.599562883377075, 2.3699028491973877, 1.3055856227874756, 1.618630290031433, 1.5923370122909546, 2.2431886196136475, 1.4876452684402466, 1.7844423055648804, 1.9117803573608398, 1.5535595417022705, 1.5489259958267212, 2.265329122543335, 1.433077335357666, 2.4788408279418945, 3.398466110229492, 1.9348931312561035, 2.204897165298462, 2.2256863117218018, 1.6991723775863647, 2.0412838459014893, 1.3696397542953491, 2.1385374069213867, 2.1020796298980713, 1.1117138862609863, 1.5673860311508179, 2.2893502712249756, 1.3703008890151978, 2.1933553218841553, 2.3728554248809814, 1.668031930923462, 2.784727096557617, 2.2288565635681152, 2.061420440673828, 1.945559024810791, 3.1614320278167725, 2.313687801361084, 1.5923490524291992, 3.0376384258270264, 1.6314715147018433, 1.7157140970230103, 0.9783911108970642, 1.3141348361968994, 1.7758941650390625, 2.6266772747039795, 2.212354898452759, 2.813169479370117, 2.400949001312256, 2.19710373878479, 1.6648670434951782, 2.3427646160125732, 2.3992857933044434, 1.9394378662109375, 1.969281554222107, 1.8074578046798706, 2.4512736797332764, 2.2511677742004395, 3.38151478767395, 2.434131383895874, 2.7608113288879395, 1.8493164777755737, 2.112745523452759, 3.2348427772521973, 2.348139762878418, 2.701200008392334, 1.1536191701889038, 1.1702803373336792, 2.598545551300049, 1.5113388299942017, 2.6224236488342285, 2.661877393722534, 1.1568347215652466, 2.540300130844116, 2.2665867805480957, 2.9450390338897705, 1.968953013420105, 1.871196985244751, 2.0897512435913086, 1.9303356409072876, 2.653479814529419, 2.1474907398223877, 1.4343831539154053, 1.9568767547607422, 2.692316770553589, 1.6910161972045898, 1.7103919982910156, 3.730804443359375, 1.4220011234283447, 2.357161521911621, 1.5128806829452515, 2.1811981201171875, 288.68768310546875, 260.14892578125, 74.18275451660156, 195.33018493652344, 310.4725341796875, 81.03704071044922, 46.992244720458984, 181.15362548828125, 204.990234375, 103.118896484375, 345.6906433105469, 102.45654296875, 268.7117614746094, 166.37890625, 148.0348358154297, 105.5943832397461, 63.067176818847656, 183.92691040039062, 172.29473876953125, 177.56494140625, 87.9418716430664, 349.5242614746094, 125.75482177734375, 201.8475341796875, 65.07671356201172, 286.1726989746094, 181.4998779296875, 257.8842468261719, 73.9827880859375, 222.0458984375, 75.12541198730469, 284.1889343261719, 326.4290771484375, 104.23149108886719, 226.8277130126953, 72.74102020263672, 303.0817565917969, 231.03675842285156, 125.75347137451172, 165.0683135986328, 142.61328125, 217.6904296875, 283.38995361328125, 68.19775390625, 241.7321014404297, 33.895511627197266, 45.34238052368164, 96.1956787109375, 156.0739288330078, 166.8946075439453, 62.56289291381836, 240.38812255859375, 68.98342895507812, 42.023193359375, 158.50221252441406, 39.736412048339844, 71.80863189697266, 168.22911071777344, 66.24591064453125, 216.82666015625, 59.539520263671875, 260.0350341796875, 47.26333236694336, 209.9253692626953, 254.76385498046875, 152.634033203125, 103.06512451171875, 147.37733459472656, 128.78721618652344, 42.4583740234375, 303.7584228515625, 112.20342254638672, 59.770320892333984, 150.47979736328125, 141.50633239746094, 193.25405883789062, 81.21265411376953, 76.4761962890625, 154.38893127441406, 224.6131591796875, 314.0975646972656, 53.83408737182617, 300.79248046875, 268.3878173828125, 220.0786895751953, 97.85386657714844, 70.18439483642578, 194.9208984375, 41.966796875, 115.52228546142578, 230.5048065185547, 205.1629180908203, 187.2777557373047, 132.0782928466797, 124.09996032714844, 136.1723175048828, 37.830078125, 40.98048400878906, 73.27410888671875, 121.91436004638672, 204.23350524902344, 134.44447326660156, 89.01199340820312, 192.576171875, 104.56798553466797, 201.0011749267578, 51.19512939453125, 121.8996353149414, 226.4775390625, 202.7012481689453, 279.1001892089844, 233.84530639648438, 176.7025146484375, 78.6168212890625, 174.09092712402344, 348.7579650878906, 167.6091766357422, 194.98580932617188, 165.889404296875, 198.54718017578125, 263.7709045410156, 238.59539794921875, 80.36293029785156, 43.16546630859375, 213.51416015625, 320.63873291015625, 168.18272399902344, 207.7585906982422, 336.6789245605469, 55.74993896484375, 356.220458984375, 185.17295837402344, 58.19131851196289, 129.9365234375, 33.55328369140625, 260.2174072265625, 110.93687438964844, 71.37555694580078, 153.1342010498047, 222.24131774902344, 187.09765625, 158.86721801757812, 262.06109619140625, 179.98692321777344, 45.908016204833984, 76.15621948242188, 85.38832092285156, 98.1617431640625, 33.141502380371094, 116.76224517822266, 123.320556640625, 147.45199584960938, 255.05674743652344, 224.2283172607422, 32.91986846923828, 39.97451400756836, 65.59323120117188, 31.346927642822266, 58.01904296875, 246.6991729736328, 63.98066329956055, 190.9516143798828, 193.4235382080078, 236.80967712402344, 354.36273193359375, 59.825584411621094, 193.0296630859375, 210.15432739257812, 241.74432373046875, 284.9176025390625, 107.05402374267578, 157.36181640625, 242.4512481689453, 157.89276123046875, 136.66488647460938, 135.295166015625, 168.4851531982422, 198.92686462402344, 27.853944778442383, 100.37532806396484, 353.1612854003906, 51.0091552734375, 206.38967895507812, 64.54413604736328, 48.651458740234375, 145.29542541503906, 138.81248474121094, 33.48248291015625, 174.4022979736328, 136.75833129882812, 122.56878662109375, 82.14025115966797, 283.3558654785156, 83.11907958984375, 175.9384307861328, 187.19839477539062, 477.6385498046875, 191.8358612060547, 92.58550262451172, 145.19505310058594, 392.16217041015625, 169.70437622070312, 101.87103271484375, 231.6001739501953, 34.64724349975586, 242.5507354736328, 124.42119598388672, 115.21157836914062, 50.528076171875, 294.1418151855469, 54.8287353515625, 67.140869140625, 153.54638671875, 47.33856201171875, 145.08413696289062, 40.709228515625, 359.6605529785156, 123.32392120361328, 93.55609893798828, 234.5408935546875, 93.49488830566406, 74.11983489990234, 286.7514343261719, 418.4738464355469, 154.28475952148438, 150.9715576171875, 205.14944458007812, 190.88507080078125, 106.405029296875, 79.037109375, 238.39910888671875, 42.167293548583984, 147.84181213378906, 80.69801330566406, 379.6619567871094, 59.44215774536133, 179.91661071777344, 144.78768920898438, 94.39398193359375, 172.67730712890625, 232.83421325683594, 56.964481353759766, 33.494384765625, 88.37786865234375, 204.58526611328125, 53.37075424194336, 161.9466552734375, 105.0087890625, 93.81861114501953, 463.737060546875, 154.37896728515625, 34.78396224975586, 378.6681213378906, 55.84351348876953, 119.1706771850586, 166.22201538085938, 116.6571273803711, 137.649169921875, 310.75732421875, 219.2768096923828, 284.9788818359375, 55.74997329711914, 172.2401885986328, 256.30340576171875, 155.53672790527344, 158.5521240234375, 40.01897430419922, 93.43289947509766, 28.212982177734375, 84.66890716552734, 111.1053466796875, 226.5828399658203, 113.45098114013672, 343.3446350097656, 183.13916015625, 438.9749755859375, 85.6623306274414, 45.92035675048828, 154.73028564453125, 160.9178924560547, 157.10606384277344, 33.99432373046875, 254.2114715576172, 154.0272674560547, 206.6461639404297, 206.9600372314453, 265.2796325683594, 115.0341796875, 31.58953857421875, 74.62713623046875, 171.4829864501953, 97.23162841796875, 116.7796630859375, 110.4510498046875, 100.833251953125, 74.10247802734375, 72.240234375, 148.57765197753906, 32.40643310546875, 40.83758544921875, 2.3212649822235107, 2.4525365829467773, 3.0805346965789795, 2.857287645339966, 2.4038994312286377, 2.3749208450317383, 2.4056482315063477, 1.3599648475646973, 1.4074572324752808, 2.7402915954589844, 1.5775060653686523, 2.1855268478393555, 2.1635141372680664, 2.2088425159454346, 1.7226312160491943, 1.9558154344558716, 2.9207048416137695, 1.5684635639190674, 3.4749462604522705, 1.9309550523757935, 3.0455691814422607, 3.6621861457824707, 1.7903379201889038, 3.530665874481201, 2.179333209991455, 2.834538459777832, 2.7669475078582764, 3.336146354675293, 2.611424446105957, 3.7924580574035645, 2.605215072631836, 2.4927356243133545, 4.183848857879639, 2.238947868347168, 1.8413641452789307, 2.6250391006469727, 1.8595589399337769, 3.28244686126709, 2.6453793048858643, 2.389111042022705, 2.615098237991333, 2.9688689708709717, 1.945021629333496, 2.6392147541046143, 2.4028234481811523, 3.576779365539551, 2.3561031818389893, 3.090517520904541, 2.1473076343536377, 3.416917562484741, 1.817879319190979, 2.227139472961426, 2.8161685466766357, 3.0795412063598633, 2.045958995819092, 3.034173011779785, 2.6152684688568115, 2.074671983718872, 2.772176742553711, 2.482274055480957, 2.3373708724975586, 1.7312008142471313, 2.9049158096313477, 1.6069614887237549, 1.9720464944839478, 1.4656037092208862, 2.546605110168457, 2.5191867351531982, 3.5172362327575684, 1.941725730895996, 2.265923500061035, 2.670731782913208, 2.7340199947357178, 3.5721638202667236, 2.505913019180298, 1.9231308698654175, 2.0609514713287354, 2.500300645828247, 2.669236898422241, 3.0816643238067627, 2.2336952686309814, 1.9146718978881836, 2.8283932209014893, 1.3820726871490479, 2.261885643005371, 3.778005838394165, 3.244973659515381, 4.22525691986084, 2.5503039360046387, 2.7825939655303955, 2.4050841331481934, 1.7181731462478638, 3.144057035446167, 2.4874513149261475, 2.2993154525756836, 2.8420841693878174, 1.5284216403961182, 3.2254762649536133, 2.6384975910186768, 2.344719409942627, 2.53695011138916, 2.589520215988159, 3.5607516765594482, 2.1501100063323975, 2.409677743911743, 2.8106935024261475, 1.3188161849975586, 2.878314256668091, 2.9012768268585205, 3.6926891803741455, 2.037980079650879, 2.2031466960906982, 2.3141698837280273, 1.4072555303573608, 1.9538450241088867, 3.0179474353790283, 3.608741044998169, 2.3574578762054443, 2.886174201965332, 2.718571186065674, 3.1915504932403564, 2.0038328170776367, 1.8693575859069824, 2.6826305389404297, 2.322805404663086, 1.775493860244751, 2.4694130420684814, 3.302096366882324, 2.474782705307007, 1.3547066450119019, 3.0546247959136963, 1.9348214864730835, 2.8861119747161865, 2.183844566345215, 2.358517646789551, 2.381577491760254, 2.7112250328063965, 3.1345577239990234, 1.1907626390457153, 2.216794967651367, 3.0741851329803467, 1.828804850578308, 2.2555389404296875, 3.2339928150177, 1.8158645629882812, 1.8459478616714478, 2.773876190185547, 1.6878494024276733, 2.222322702407837, 2.690488338470459, 2.447039842605591, 2.0743093490600586, 2.62581467628479, 3.3593382835388184, 1.3611918687820435, 2.2439968585968018, 2.6579015254974365, 3.5370869636535645, 1.995871901512146, 2.7104601860046387, 2.2240285873413086, 2.5433225631713867, 3.128643751144409, 3.584393262863159, 2.923316478729248, 3.4656779766082764, 2.801677703857422, 1.8090816736221313, 2.7146899700164795, 2.175065279006958, 2.1770124435424805, 1.9676581621170044, 2.8907806873321533, 2.4226388931274414, 3.0847387313842773, 2.539912700653076, 2.759273052215576, 2.028064012527466, 3.295140504837036, 2.79757022857666, 2.4867048263549805, 2.5872912406921387, 1.6957731246948242, 2.2117221355438232, 1.4634275436401367, 2.3349313735961914, 1.8188451528549194, 2.7377099990844727, 2.9585282802581787, 2.858020305633545, 2.966162919998169, 4.690736770629883, 2.18845272064209, 1.5948189496994019, 3.349436044692993, 2.793793201446533, 1.974192500114441, 2.655108690261841, 2.814387559890747, 2.112910509109497, 2.263188362121582, 3.1030468940734863, 1.4635299444198608, 2.64974308013916, 2.1272246837615967, 2.316563606262207, 1.9638384580612183, 1.7832344770431519, 3.003649950027466, 2.3435277938842773, 1.9160170555114746, 1.9011203050613403, 2.682276964187622, 2.2842626571655273, 3.5241594314575195, 2.157649040222168, 2.5660622119903564, 3.4251530170440674, 1.6737737655639648, 2.8257439136505127, 1.8312047719955444, 2.4241995811462402, 2.6087188720703125, 2.369544506072998, 2.6018877029418945, 2.901494026184082, 2.2685110569000244, 1.9013962745666504, 2.429100275039673, 2.1010525226593018, 2.6367692947387695, 3.09070086479187, 1.090590476989746, 2.8680334091186523, 2.6501762866973877, 2.9828522205352783, 2.1650285720825195, 2.052975654602051, 1.971716284751892, 3.1329259872436523, 3.8042690753936768, 2.006714105606079, 3.26774263381958, 3.6507885456085205, 2.157235860824585, 2.587236166000366, 4.123553276062012, 3.331820487976074, 2.3690364360809326, 2.4718637466430664, 1.2799066305160522, 3.141228199005127, 1.8693877458572388, 1.5897107124328613, 2.07033634185791, 2.431612730026245, 2.1895627975463867, 1.3971093893051147, 2.427962303161621, 1.4979568719863892, 1.8292511701583862, 2.114875078201294, 1.761397361755371, 2.759222984313965, 2.644365072250366, 1.8827085494995117, 3.572627067565918, 2.178135395050049, 1.7355451583862305, 2.403137683868408, 2.21468448638916, 3.649463176727295, 1.6222127676010132, 2.292790412902832, 1.7003164291381836, 3.0203983783721924, 2.651780366897583, 3.1262309551239014, 3.0969879627227783, 1.5667775869369507, 1.6152706146240234, 1.8507829904556274, 2.715787410736084, 3.795924663543701, 2.9220898151397705, 3.57307767868042, 2.143876075744629, 2.496628761291504, 1.9370368719100952, 1.223827600479126, 3.6643054485321045, 1.9278135299682617, 2.713404417037964, 1.2557278871536255, 3.3868188858032227, 2.309931993484497, 1.9956679344177246, 2.587557554244995, 2.587902545928955, 2.4271535873413086, 0.20617465674877167, 0.19495660066604614, 0.17789167165756226, 0.17839963734149933, 0.24010880291461945, 0.20171645283699036, 0.22509200870990753, 0.28483647108078003, 0.2653997838497162, 0.22128313779830933, 0.22946031391620636, 0.21395133435726166, 0.2311619520187378, 0.25523313879966736, 0.17288541793823242, 0.26003822684288025, 0.20002582669258118, 0.21655501425266266, 0.25188302993774414, 0.16458262503147125, 0.21362362802028656, 0.2269146740436554, 0.21497176587581635, 0.16106677055358887, 0.21014094352722168, 0.1834959238767624, 0.1470516324043274, 0.19829070568084717, 0.1923791915178299, 0.20381751656532288, 0.20800375938415527, 0.2429400235414505, 0.20793287456035614, 0.17463040351867676, 0.17414550483226776, 0.13943558931350708, 0.18997535109519958, 0.2058771848678589, 0.2401365041732788, 0.23364554345607758, 0.22943098843097687, 0.20392179489135742, 0.22194012999534607, 0.21465685963630676, 0.17884890735149384, 0.22033734619617462, 0.23471038043498993, 0.19069457054138184, 0.13741308450698853, 0.2591228783130646, 0.26125383377075195, 0.20508834719657898, 0.2085336446762085, 0.19579389691352844, 0.2368064820766449, 0.18768592178821564, 0.20416328310966492, 0.23601838946342468, 0.1853286772966385, 0.26772645115852356, 0.21454773843288422, 0.1671844869852066, 0.277399480342865, 0.19447463750839233, 0.12173571437597275, 0.1987200826406479, 0.213430717587471, 0.21339240670204163, 0.21886895596981049, 0.23540887236595154, 0.13775475323200226, 0.24931003153324127, 0.15145792067050934, 0.16400215029716492, 0.2678699195384979, 0.1919112503528595, 0.21874922513961792, 0.280864417552948, 0.2575957477092743, 0.17574958503246307, 0.19031882286071777, 0.2725425958633423, 0.14963474869728088, 0.22607608139514923, 0.1733178347349167, 0.23691295087337494, 0.24641908705234528, 0.20069003105163574, 0.22833500802516937, 0.2493375986814499, 0.2225906252861023, 0.27139192819595337, 0.21801680326461792, 0.20839031040668488, 0.20003308355808258, 0.23456473648548126, 0.14894531667232513, 0.2040625363588333, 0.2059653103351593, 0.1689181625843048, 0.24884666502475739, 0.22000455856323242, 0.15385130047798157, 0.15714138746261597, 0.19459989666938782, 0.17623834311962128, 0.22630943357944489, 0.25418969988822937, 0.17334899306297302, 0.23238158226013184, 0.20242400467395782, 0.14442776143550873, 0.22764289379119873, 0.20883223414421082, 0.2612610459327698, 0.23501817882061005, 0.2559095621109009, 0.18275737762451172, 0.16629554331302643, 0.23871153593063354, 0.21931181848049164, 0.2595682442188263, 0.18726029992103577, 0.24614763259887695, 0.15916647017002106, 0.24760407209396362, 0.17384465038776398, 0.24752330780029297, 0.2109125256538391, 0.21519112586975098, 0.1832863986492157, 0.20022760331630707, 0.1742556095123291, 0.18835730850696564, 0.2500322759151459, 0.22084270417690277, 0.27717143297195435, 0.15948936343193054, 0.19434070587158203, 0.19197936356067657, 0.23393011093139648, 0.16240495443344116, 0.20947301387786865, 0.20288394391536713, 0.21441127359867096, 0.20711322128772736, 0.23502999544143677, 0.20152638852596283, 0.19782283902168274, 0.24664390087127686, 0.24420039355754852, 0.200021892786026, 0.1915007382631302, 0.2072221338748932, 0.21207332611083984, 0.2103709578514099, 0.17227418720722198, 0.23751002550125122, 0.202886164188385, 0.2276669293642044, 0.15245875716209412, 0.21292056143283844, 0.2546687722206116, 0.25081339478492737, 0.20417240262031555, 0.1933155357837677, 0.20581579208374023, 0.201857790350914, 0.1992938220500946, 0.20504797995090485, 0.20187006890773773, 0.26264721155166626, 0.21152137219905853, 0.16836236417293549, 0.17203406989574432, 0.16940784454345703, 0.23193728923797607, 0.17425517737865448, 0.1585366129875183, 0.2789056599140167, 0.2861323356628418, 0.2630046606063843, 0.22999899089336395, 0.11781730502843857, 0.24790620803833008, 0.2581374943256378, 0.1715756207704544, 0.22535067796707153, 0.20732669532299042, 0.16096824407577515, 0.3016006648540497, 0.23115956783294678, 0.16855856776237488, 0.21094392240047455, 0.2129024863243103, 0.16888995468616486, 0.24459433555603027, 0.24758417904376984, 0.16710083186626434, 0.13534101843833923, 0.1755838692188263, 0.22321979701519012, 0.18652038276195526, 0.2307892143726349, 0.2510818839073181, 0.1965472251176834, 0.16084223985671997, 0.2096170336008072, 0.1727859079837799, 0.21243566274642944, 0.24832852184772491, 0.17366571724414825, 0.18330787122249603, 0.2023080587387085, 0.25210174918174744, 0.2549130916595459, 0.2245287448167801, 0.25791022181510925, 0.3217928111553192, 0.17639967799186707, 0.24888843297958374, 0.2262640744447708, 0.2020835131406784, 0.229756161570549, 0.18990062177181244, 0.22443059086799622, 0.176858589053154, 0.20398768782615662, 0.21056567132472992, 0.2823469936847687, 0.28229111433029175, 0.16138172149658203, 0.21095113456249237, 0.18170787394046783, 0.21832935512065887, 0.22808994352817535, 0.2147420048713684, 0.22495852410793304, 0.24164438247680664, 0.16143514215946198, 0.24357669055461884, 0.21883270144462585, 0.1437532901763916, 0.1658802330493927, 0.19050846993923187, 0.23313429951667786, 0.22853882610797882, 0.16539396345615387, 0.21008136868476868, 0.25071704387664795, 0.21105167269706726, 0.09773466736078262, 0.1507956087589264, 0.23784856498241425, 0.22869448363780975, 0.20362992584705353, 0.27250581979751587, 0.23200786113739014, 0.1506914645433426, 0.17067980766296387, 0.27039778232574463, 0.23601743578910828, 0.17486436665058136, 0.18333199620246887, 0.2010374814271927, 0.18663237988948822, 0.186906099319458, 0.17231790721416473, 0.18611285090446472, 0.25392162799835205, 0.22914431989192963, 0.19947698712348938, 0.26858317852020264, 0.2642256021499634, 0.2236066609621048, 0.27439045906066895, 0.23795294761657715, 0.18887321650981903, 0.23214960098266602, 0.1814885288476944, 0.26657021045684814, 0.24102142453193665, 0.19582805037498474, 0.21074916422367096, 0.16263984143733978, 0.15709546208381653, 0.20581750571727753, 0.19600501656532288, 0.15423275530338287, 0.2954787313938141, 0.19095639884471893, 0.2503218352794647, 0.3247140049934387, 0.20441024005413055, 0.14054128527641296, 0.20572249591350555, 0.25439968705177307, 0.17391790449619293, 0.18130815029144287, 0.21031156182289124, 2.3922085762023926, 1.865736961364746, 2.6450085639953613, 2.1269426345825195, 2.520555257797241, 2.4872190952301025, 1.4968852996826172, 1.4936250448226929, 2.3555407524108887, 2.9593420028686523, 2.2359306812286377, 2.3557446002960205, 3.257680892944336, 1.4880949258804321, 3.2411820888519287, 2.156647205352783, 1.8509445190429688, 1.8861021995544434, 2.9211959838867188, 2.3157527446746826, 1.5065195560455322, 1.5472424030303955, 2.282244920730591, 1.3331447839736938, 2.2819302082061768, 1.5420244932174683, 2.6753432750701904, 2.356260299682617, 1.251826286315918, 1.6277493238449097, 2.4065539836883545, 2.2283012866973877, 2.4580230712890625, 1.2915352582931519, 1.8144158124923706, 2.0830633640289307, 2.7365663051605225, 2.4647397994995117, 1.7142893075942993, 2.728330612182617, 2.994154214859009, 1.6019115447998047, 2.121976852416992, 1.3387222290039062, 1.8172613382339478, 2.3080382347106934, 2.664710521697998, 1.9390528202056885, 2.2555882930755615, 2.2125184535980225, 2.33292293548584, 1.70430326461792, 2.2983226776123047, 1.4719860553741455, 1.8593406677246094, 1.4603341817855835, 2.197925329208374, 2.6162431240081787, 1.6054290533065796, 2.590590238571167, 1.777329921722412, 2.8080356121063232, 2.0071451663970947, 2.6193177700042725, 2.6369917392730713, 1.8291971683502197, 1.494649887084961, 2.2013533115386963, 2.329340696334839, 1.5818941593170166, 1.7475271224975586, 2.529670000076294, 2.346296548843384, 1.397713303565979, 2.155747413635254, 1.8098951578140259, 1.3728290796279907, 2.563164234161377, 2.052546501159668, 1.8578071594238281, 2.359312057495117, 1.5977404117584229, 1.5921227931976318, 2.611868143081665, 2.276965856552124, 2.188817024230957, 2.1349291801452637, 2.735278844833374, 2.5719213485717773, 1.9044348001480103, 1.7857407331466675, 2.2200164794921875, 1.5684890747070312, 2.182424545288086, 2.1830732822418213, 2.232996702194214, 2.0942068099975586, 2.8132236003875732, 2.8569371700286865, 1.26899254322052, 2.275745391845703, 2.5136218070983887, 2.1759119033813477, 2.351749897003174, 1.5624128580093384, 1.5908252000808716, 1.312389612197876, 3.2684502601623535, 1.2885628938674927, 2.145334005355835, 1.5431817770004272, 2.2923409938812256, 1.9958540201187134, 1.8652185201644897, 2.272841215133667, 1.946382999420166, 1.8869686126708984, 2.0398526191711426, 1.7386938333511353, 1.8846582174301147, 2.457617998123169, 2.3189876079559326, 1.8830572366714478, 2.1493794918060303, 2.1783459186553955, 1.5637530088424683, 2.282255172729492, 2.0364058017730713, 1.7749871015548706, 2.619924306869507, 1.6302083730697632, 1.503249168395996, 2.0694379806518555, 1.885787010192871, 2.0466952323913574, 2.240344524383545, 1.4330999851226807, 1.7727998495101929, 2.1295883655548096, 2.960923910140991, 2.663090229034424, 2.6164891719818115, 2.361079454421997, 1.631245493888855, 1.8481107950210571, 2.0490059852600098, 2.938307523727417, 1.804948329925537, 2.5391247272491455, 2.7415618896484375, 1.9342235326766968, 1.576075553894043, 2.6198713779449463, 2.533419370651245, 2.4958746433258057, 1.694604754447937, 2.8070483207702637, 3.0671162605285645, 1.2797036170959473, 2.0734519958496094, 1.8221043348312378, 2.558861255645752, 2.275555372238159, 3.905569314956665, 3.153245210647583, 2.7246477603912354, 2.155453681945801, 3.227492570877075, 2.436048984527588, 2.0922398567199707, 2.1248321533203125, 1.4155536890029907, 2.211827278137207, 1.5976258516311646, 2.401169776916504, 2.802598714828491, 2.0918617248535156, 3.011855363845825, 1.407418131828308, 2.4428887367248535, 1.8499093055725098, 2.316642999649048, 2.552245616912842, 1.9703317880630493, 1.8141300678253174, 2.829657793045044, 1.8654766082763672, 2.497500419616699, 1.7455549240112305, 2.575986862182617, 1.9605817794799805, 1.0970568656921387, 1.5801982879638672, 2.246882677078247, 1.875657558441162, 2.4933769702911377, 2.6963887214660645, 1.9245179891586304, 1.7750405073165894, 1.3046026229858398, 3.162541389465332, 2.158168315887451, 1.7252705097198486, 1.8621952533721924, 2.0630481243133545, 1.6637026071548462, 2.3482704162597656, 2.1241402626037598, 2.3923182487487793, 1.3167269229888916, 1.2265805006027222, 2.324781656265259, 2.2621800899505615, 2.3177313804626465, 1.8650823831558228, 2.0830130577087402, 2.312664031982422, 1.5208532810211182, 2.638397693634033, 1.83251953125, 2.1651206016540527, 1.646404504776001, 1.7995071411132812, 1.7108951807022095, 2.6034910678863525, 2.436765670776367, 1.2955492734909058, 1.1726758480072021, 1.2631278038024902, 1.5460337400436401, 2.470126152038574, 1.8576580286026, 2.0876104831695557, 3.1079330444335938, 2.3272576332092285, 2.3341493606567383, 1.6830227375030518, 1.1535700559616089, 2.387399196624756, 2.3021035194396973, 2.010788917541504, 3.101598024368286, 1.6622627973556519, 2.5563716888427734, 2.2090249061584473, 1.988359808921814, 1.9677540063858032, 2.0496861934661865, 1.535683274269104, 2.8388805389404297, 2.1339011192321777, 2.0185704231262207, 1.7221364974975586, 1.951541543006897, 1.8929345607757568, 2.5431857109069824, 1.8729826211929321, 3.2787041664123535, 2.053243637084961, 1.8070793151855469, 2.545787811279297, 2.6687285900115967, 2.4816195964813232, 2.2307562828063965, 2.522071123123169, 2.2006893157958984, 1.7728512287139893, 1.527524709701538, 1.590242862701416, 1.7888103723526, 2.1566007137298584, 2.0704641342163086, 3.326138734817505, 1.9505878686904907, 2.3328943252563477, 1.665590524673462, 1.2731499671936035, 1.9539175033569336, 1.5899988412857056, 1.2780486345291138, 2.018810510635376, 2.2640016078948975, 1.9736230373382568, 2.9434802532196045, 2.5031914710998535, 2.144540786743164, 2.9867947101593018, 2.838045597076416, 2.3774359226226807, 1.971036672592163, 2.2335915565490723, 2.7836930751800537, 2.663801908493042, 2.031724691390991, 2.2096714973449707, 3.5650405883789062, 2.5781829357147217, 1.5607863664627075, 2.2203879356384277, 2.380398750305176, 98.20548248291016, 152.0170440673828, 201.6122283935547, 64.388427734375, 80.52315521240234, 172.84063720703125, 206.3873748779297, 148.28195190429688, 89.92572021484375, 225.9246826171875, 143.86573791503906, 63.75140380859375, 195.0060577392578, 170.1600799560547, 117.79732513427734, 128.32568359375, 62.431297302246094, 91.94005584716797, 216.81651306152344, 75.2975845336914, 170.06222534179688, 213.33755493164062, 251.36346435546875, 99.68087768554688, 136.09091186523438, 105.79510498046875, 226.94493103027344, 260.1944580078125, 150.47418212890625, 186.7518768310547, 83.03302764892578, 278.3283386230469, 124.0718994140625, 318.6158447265625, 126.71345520019531, 153.34629821777344, 219.20263671875, 113.9154052734375, 182.01007080078125, 171.302490234375, 195.7329864501953, 222.84912109375, 274.58740234375, 86.33343505859375, 242.16717529296875, 49.77815246582031, 307.0274658203125, 93.96263122558594, 272.72711181640625, 80.0447998046875, 130.36721801757812, 150.0236358642578, 138.36993408203125, 183.9514923095703, 90.56375122070312, 197.02171325683594, 76.63634490966797, 131.5130615234375, 159.515380859375, 121.01036834716797, 71.09143829345703, 83.57122802734375, 25.6229248046875, 218.28656005859375, 163.80877685546875, 174.96157836914062, 80.25080108642578, 222.48092651367188, 224.4268341064453, 311.0558776855469, 37.4122314453125, 134.7259521484375, 214.93386840820312, 139.19805908203125, 48.25452423095703, 83.71282958984375, 36.30304718017578, 227.28831481933594, 134.30271911621094, 35.05670166015625, 39.90533447265625, 168.1785888671875, 43.79319381713867, 59.49087905883789, 142.96205139160156, 117.50164794921875, 84.99529266357422, 104.88232421875, 250.2427520751953, 161.2970733642578, 110.66342163085938, 168.491943359375, 231.73643493652344, 246.799072265625, 157.9567108154297, 97.00664520263672, 274.3915100097656, 200.70469665527344, 179.6363983154297, 166.13229370117188, 274.6348876953125, 122.365478515625, 220.9505615234375, 42.81261444091797, 163.8837127685547, 266.23297119140625, 97.91997528076172, 137.7941436767578, 154.64682006835938, 52.8245849609375, 30.584197998046875, 266.65673828125, 314.86627197265625, 265.779052734375, 58.578582763671875, 398.7947692871094, 89.4896240234375, 213.09197998046875, 89.28304290771484, 76.3359375, 146.44491577148438, 60.02020263671875, 50.23013687133789, 408.0643005371094, 133.01751708984375, 261.47760009765625, 231.64569091796875, 136.21380615234375, 41.056884765625, 79.41331481933594, 232.15521240234375, 92.4637451171875, 79.99505615234375, 89.56195068359375, 35.892578125, 433.4693908691406, 134.3685302734375, 303.81549072265625, 81.80101776123047, 129.28216552734375, 187.61721801757812, 255.09490966796875, 92.46685028076172, 52.48694610595703, 140.86224365234375, 305.13031005859375, 223.3922576904297, 57.8131103515625, 124.8399658203125, 283.249755859375, 107.88495635986328, 36.0252685546875, 336.426513671875, 184.52268981933594, 400.56976318359375, 170.03375244140625, 134.3876495361328, 39.74428939819336, 121.20113372802734, 84.48452758789062, 238.9261474609375, 113.6053466796875, 283.9520263671875, 134.9864044189453, 77.1846923828125, 39.05717849731445, 48.44775390625, 49.7244873046875, 392.8246154785156, 110.3494873046875, 293.9670715332031, 85.0257568359375, 106.23451232910156, 92.52213287353516, 283.39007568359375, 169.35406494140625, 107.73072814941406, 262.04693603515625, 244.1854705810547, 98.46611785888672, 93.86671447753906, 107.16072845458984, 229.048583984375, 123.56938934326172, 64.2694091796875, 301.1116638183594, 38.8408203125, 229.65887451171875, 302.35772705078125, 198.03057861328125, 130.46446228027344, 226.8648223876953, 279.25518798828125, 49.98382568359375, 226.3710479736328, 95.03105926513672, 33.05410385131836, 154.8903045654297, 315.99945068359375, 189.27561950683594, 34.689762115478516, 245.3153076171875, 67.35037231445312, 453.11749267578125, 226.552490234375, 238.0069122314453, 89.21733856201172, 127.60845184326172, 217.89358520507812, 88.33818817138672, 102.65189361572266, 127.89298248291016, 291.8923645019531, 108.95171356201172, 117.22896575927734, 152.0634307861328, 128.5609893798828, 229.76287841796875, 48.607391357421875, 54.83148193359375, 38.607059478759766, 144.16900634765625, 121.21495819091797, 179.5320281982422, 85.0321044921875, 181.626953125, 158.46261596679688, 142.88470458984375, 105.49136352539062, 108.44884490966797, 102.02550506591797, 63.7650146484375, 237.9295196533203, 40.03871536254883, 299.1112060546875, 84.98448944091797, 58.76920700073242, 72.17575073242188, 100.19097137451172, 397.07171630859375, 40.226165771484375, 326.8790283203125, 153.1590576171875, 84.56082153320312, 175.20730590820312, 80.24333190917969, 35.70570373535156, 324.73443603515625, 245.1299591064453, 197.37136840820312, 59.89069747924805, 298.2777404785156, 181.2787628173828, 306.64483642578125, 279.55194091796875, 38.548309326171875, 46.443416595458984, 145.4725341796875, 44.89478302001953, 119.78948974609375, 110.09064483642578, 142.41448974609375, 117.8861312866211, 38.40285873413086, 54.11029052734375, 132.1153106689453, 44.955379486083984, 159.877197265625, 220.6527099609375, 40.42987060546875, 340.3318786621094, 140.583984375, 281.97137451171875, 66.12175750732422, 206.8128662109375, 83.91484069824219, 48.90790939331055, 39.0257568359375, 70.79054260253906, 107.34220123291016, 168.46144104003906, 497.9920654296875, 160.6057891845703, 115.04077911376953, 118.86856842041016, 374.71026611328125, 176.11245727539062, 31.637929916381836, 173.59732055664062, 299.6800842285156, 111.8949203491211, 278.7364807128906, 51.434818267822266, 92.89331817626953, 169.00694274902344, 44.34328842163086, 213.6922149658203, 39.52426528930664, 96.07964324951172, 374.7732849121094, 4.164638996124268, 2.5253024101257324, 1.94136381149292, 1.7430753707885742, 2.3369357585906982, 1.9268670082092285, 1.929013967514038, 2.3559179306030273, 3.487042188644409, 2.560870409011841, 3.0890722274780273, 3.3723278045654297, 2.628037691116333, 2.284572124481201, 3.1128859519958496, 2.1015539169311523, 1.666035532951355, 3.3898515701293945, 1.5958129167556763, 2.0433425903320312, 2.258072853088379, 1.4005829095840454, 2.6456246376037598, 3.2909305095672607, 2.5208652019500732, 1.8515949249267578, 2.9022789001464844, 1.6560888290405273, 2.053222894668579, 2.6855249404907227, 1.251453161239624, 3.2609236240386963, 1.2687348127365112, 1.8114978075027466, 1.8969429731369019, 2.9961864948272705, 1.7757922410964966, 2.1429953575134277, 2.933216094970703, 1.1160926818847656, 3.8568830490112305, 4.305232048034668, 2.3147366046905518, 3.4050402641296387, 3.117978096008301, 3.034910202026367, 3.1949944496154785, 2.5651257038116455, 2.2302238941192627, 2.013566493988037, 3.192478656768799, 3.2666549682617188, 2.1295087337493896, 2.920304536819458, 2.08819317817688, 2.5355634689331055, 2.5845909118652344, 3.0241756439208984, 2.1387033462524414, 2.119816780090332, 2.499546527862549, 1.8510493040084839, 3.0773136615753174, 3.051692247390747, 1.7415817975997925, 2.009213447570801, 2.703026056289673, 2.0479631423950195, 2.8733348846435547, 3.2961788177490234, 1.6031484603881836, 2.112921953201294, 2.8734242916107178, 2.4641451835632324, 3.9239628314971924, 2.684490919113159, 1.7934426069259644, 1.8296732902526855, 1.719746470451355, 2.12894344329834, 2.4388201236724854, 2.2439818382263184, 1.4400299787521362, 3.1650054454803467, 3.6282126903533936, 2.1140496730804443, 2.129197120666504, 2.5829124450683594, 2.077733039855957, 2.603787422180176, 2.7196874618530273, 2.3957719802856445, 3.0255181789398193, 2.2776939868927, 2.735166549682617, 2.486802101135254, 3.1980066299438477, 1.8179311752319336, 2.7176952362060547, 3.4119768142700195, 3.414719581604004, 3.0298075675964355, 1.4713181257247925, 2.3761627674102783, 3.0430424213409424, 3.173832416534424, 2.807685136795044, 2.229506492614746, 3.292973279953003, 3.401287794113159, 1.7317322492599487, 3.497267961502075, 3.305370330810547, 3.1619060039520264, 2.9346401691436768, 2.523548126220703, 1.6617194414138794, 1.8143749237060547, 1.948217749595642, 2.806657075881958, 2.455875873565674, 2.202235221862793, 3.585416078567505, 2.2062368392944336, 3.29860782623291, 2.075892448425293, 2.947781801223755, 2.6955974102020264, 2.3711977005004883, 3.6359927654266357, 3.603196382522583, 1.6234651803970337, 2.54321551322937, 2.7040929794311523, 2.484757423400879, 3.1294033527374268, 2.450016975402832, 3.0964648723602295, 2.320828437805176, 1.8955533504486084, 2.333693504333496, 2.5628576278686523, 2.4768741130828857, 2.391023874282837, 2.6058855056762695, 2.7199907302856445, 2.535231351852417, 1.9808704853057861, 2.4232876300811768, 3.069530963897705, 2.8999571800231934, 2.0370988845825195, 2.9599316120147705, 2.00948429107666, 3.712294816970825, 1.9161499738693237, 2.350543975830078, 1.5441808700561523, 2.6686737537384033, 2.1613988876342773, 1.760823130607605, 2.306900978088379, 1.8443785905838013, 4.3080573081970215, 3.051093101501465, 1.9654701948165894, 2.7722859382629395, 2.83937931060791, 3.3480772972106934, 2.4631569385528564, 3.1125946044921875, 2.879276752471924, 2.798192024230957, 3.2462077140808105, 1.9255279302597046, 2.0918188095092773, 2.228569746017456, 1.698548674583435, 2.6303417682647705, 2.4882326126098633, 2.926992177963257, 2.87717342376709, 2.7398486137390137, 3.3433544635772705, 2.7521092891693115, 1.324432611465454, 2.233421802520752, 2.980670213699341, 4.066203594207764, 2.5377588272094727, 1.5757784843444824, 2.431565999984741, 1.5678637027740479, 3.15598201751709, 2.766737937927246, 2.7303524017333984, 2.388129234313965, 2.75431752204895, 2.2344605922698975, 2.8584446907043457, 2.206376075744629, 1.8782415390014648, 1.6852272748947144, 2.8480310440063477, 2.018653631210327, 2.203139305114746, 1.962640643119812, 2.0326943397521973, 3.0438148975372314, 2.6717467308044434, 3.149981737136841, 1.9623931646347046, 2.289158821105957, 2.4588656425476074, 2.6155407428741455, 2.526529550552368, 3.0782482624053955, 1.5419442653656006, 2.5070865154266357, 3.676692485809326, 2.0194616317749023, 2.5866284370422363, 2.8839938640594482, 2.1245012283325195, 3.903689384460449, 2.231872320175171, 1.9822317361831665, 2.846254825592041, 3.062751054763794, 1.6296141147613525, 2.7949328422546387, 1.7259855270385742, 2.5391488075256348, 3.4292094707489014, 1.8805047273635864, 3.413937568664551, 2.5569276809692383, 3.4682493209838867, 3.1527469158172607, 3.5912084579467773, 1.636648178100586, 2.2284135818481445, 3.6753785610198975, 1.9080091714859009, 3.252488136291504, 3.9347310066223145, 2.2572526931762695, 2.602368116378784, 2.187614917755127, 4.034534931182861, 1.7920221090316772, 3.5387487411499023, 3.9437971115112305, 2.2704458236694336, 2.3057069778442383, 1.310060977935791, 2.531541109085083, 2.557887315750122, 2.2518224716186523, 2.479877471923828, 1.7982529401779175, 2.1555776596069336, 3.1218478679656982, 1.912734031677246, 3.0983476638793945, 2.103128671646118, 2.42368221282959, 2.2473466396331787, 2.1536285877227783, 2.6810271739959717, 2.189846992492676, 2.6450469493865967, 2.00913143157959, 3.0304253101348877, 3.0440280437469482, 2.3451623916625977, 2.163496971130371, 1.9690545797348022, 1.967305064201355, 2.751417875289917, 2.326716423034668, 3.7083141803741455, 3.91032338142395, 1.6643670797348022, 1.8287725448608398, 3.6555302143096924, 2.602656841278076, 2.5238864421844482, 2.350338935852051, 2.210775136947632, 2.785902976989746, 1.7464417219161987, 2.341933488845825, 2.1190972328186035, 2.149775505065918, 1.6506234407424927, 2.0549468994140625, 2.0966081619262695, 2.5087647438049316, 3.6580212116241455, 0.17847521603107452, 0.24652686715126038, 0.2554011642932892, 0.2104218602180481, 0.19937801361083984, 0.14057622849941254, 0.1452854424715042, 0.12133317440748215, 0.20133741199970245, 0.21893662214279175, 0.1391775906085968, 0.2351803481578827, 0.21743667125701904, 0.1847444623708725, 0.2628903090953827, 0.16060569882392883, 0.2282918095588684, 0.1710154116153717, 0.21213479340076447, 0.23284335434436798, 0.20126254856586456, 0.2793687880039215, 0.15640336275100708, 0.19248859584331512, 0.20228606462478638, 0.22786270081996918, 0.2107773870229721, 0.15111449360847473, 0.2099340409040451, 0.1407075822353363, 0.23528464138507843, 0.1921694576740265, 0.1944352239370346, 0.1927831619977951, 0.22582732141017914, 0.26635316014289856, 0.20036624372005463, 0.27729660272598267, 0.26186472177505493, 0.20633037388324738, 0.21159982681274414, 0.16908715665340424, 0.23607081174850464, 0.23065009713172913, 0.22725479304790497, 0.16309985518455505, 0.31185224652290344, 0.21422235667705536, 0.18854713439941406, 0.2125653475522995, 0.2004171758890152, 0.2789534330368042, 0.1653153896331787, 0.24681496620178223, 0.13753743469715118, 0.22929637134075165, 0.18466778099536896, 0.14444805681705475, 0.2777445912361145, 0.2693132758140564, 0.2406289428472519, 0.21428756415843964, 0.16817925870418549, 0.18130095303058624, 0.244818314909935, 0.17939890921115875, 0.2791600823402405, 0.17328830063343048, 0.23077571392059326, 0.18536467850208282, 0.1565917432308197, 0.1918516755104065, 0.23338370025157928, 0.1572207510471344, 0.2566449046134949, 0.18844051659107208, 0.19863823056221008, 0.2269044816493988, 0.22688715159893036, 0.16129350662231445, 0.19289767742156982, 0.21468570828437805, 0.14157629013061523, 0.1849634200334549, 0.16083955764770508, 0.21682441234588623, 0.23636341094970703, 0.22097747027873993, 0.21593420207500458, 0.2410898357629776, 0.2224297821521759, 0.22712482511997223, 0.23666220903396606, 0.23390555381774902, 0.20318110287189484, 0.15330517292022705, 0.1978660225868225, 0.20848938822746277, 0.17665301263332367, 0.21392448246479034, 0.25345179438591003, 0.19387736916542053, 0.2401391863822937, 0.21172089874744415, 0.2612020671367645, 0.1565040946006775, 0.21944324672222137, 0.24635930359363556, 0.22826319932937622, 0.18942038714885712, 0.2548102140426636, 0.2393980175256729, 0.2647145092487335, 0.2287302315235138, 0.22416095435619354, 0.2507583498954773, 0.24138696491718292, 0.1611592024564743, 0.25936946272850037, 0.1707376092672348, 0.24356365203857422, 0.23087887465953827, 0.1561700999736786, 0.16556037962436676, 0.1472235769033432, 0.16563600301742554, 0.23164312541484833, 0.19036628305912018, 0.26187002658843994, 0.18363292515277863, 0.20578250288963318, 0.20820572972297668, 0.21500808000564575, 0.2136540561914444, 0.20024491846561432, 0.25233194231987, 0.19661760330200195, 0.20812664926052094, 0.27574461698532104, 0.19005060195922852, 0.1810029149055481, 0.15982218086719513, 0.21175086498260498, 0.24981944262981415, 0.2085857391357422, 0.1906706839799881, 0.17074143886566162, 0.1861010640859604, 0.18805812299251556, 0.13596850633621216, 0.19039423763751984, 0.20914901793003082, 0.17009258270263672, 0.17773106694221497, 0.27578455209732056, 0.22543400526046753, 0.1622374951839447, 0.13032014667987823, 0.2619463801383972, 0.15989753603935242, 0.23366683721542358, 0.2801998555660248, 0.17146086692810059, 0.20166727900505066, 0.16009223461151123, 0.2267458140850067, 0.23027372360229492, 0.2339547872543335, 0.22172945737838745, 0.2537095546722412, 0.3330996632575989, 0.1790885478258133, 0.17988185584545135, 0.22337016463279724, 0.2376059740781784, 0.1987641453742981, 0.3169615864753723, 0.22913360595703125, 0.2414046972990036, 0.18301276862621307, 0.18238750100135803, 0.24176399409770966, 0.20873621106147766, 0.20639914274215698, 0.26875802874565125, 0.22213798761367798, 0.19128547608852386, 0.23514388501644135, 0.231526181101799, 0.1964114010334015, 0.24364057183265686, 0.23063607513904572, 0.24064551293849945, 0.16835197806358337, 0.2971242368221283, 0.2036294937133789, 0.20217230916023254, 0.2284945249557495, 0.2153216302394867, 0.2163560837507248, 0.18474280834197998, 0.19561249017715454, 0.23526209592819214, 0.11217246949672699, 0.2797899544239044, 0.18225371837615967, 0.20328906178474426, 0.18439026176929474, 0.15792043507099152, 0.21772828698158264, 0.2236030548810959, 0.19261184334754944, 0.2144564837217331, 0.23174075782299042, 0.24790382385253906, 0.21051478385925293, 0.241194486618042, 0.18898558616638184, 0.20182541012763977, 0.25397780537605286, 0.2704744338989258, 0.20889568328857422, 0.26804712414741516, 0.23267357051372528, 0.2571253478527069, 0.21069097518920898, 0.21208156645298004, 0.22573399543762207, 0.20773948729038239, 0.2489081472158432, 0.1765587031841278, 0.22885115444660187, 0.2505333423614502, 0.2130061835050583, 0.16102582216262817, 0.19916078448295593, 0.22575990855693817, 0.18345263600349426, 0.21143238246440887, 0.18809695541858673, 0.20136527717113495, 0.16788676381111145, 0.2309381365776062, 0.22220443189144135, 0.2115553617477417, 0.25607892870903015, 0.22296775877475739, 0.22458696365356445, 0.2408280074596405, 0.2590413987636566, 0.18412181735038757, 0.12054634094238281, 0.21840900182724, 0.14248719811439514, 0.21524207293987274, 0.1981545239686966, 0.17327484488487244, 0.23844014108181, 0.25957781076431274, 0.20361262559890747, 0.1720980405807495, 0.22508910298347473, 0.16487345099449158, 0.16757579147815704, 0.1896076202392578, 0.22214339673519135, 0.21110987663269043, 0.21281106770038605, 0.13632184267044067, 0.23116448521614075, 0.20754067599773407, 0.21828719973564148, 0.17796210944652557, 0.2508210241794586, 0.14419245719909668, 0.24973750114440918, 0.1990298628807068, 0.22392024099826813, 0.18707092106342316, 0.1990109533071518, 0.23592425882816315, 0.302370548248291, 0.15555788576602936, 0.2284056395292282, 0.3121156692504883, 0.18495967984199524, 0.2259325236082077, 0.247776061296463, 0.1468968391418457, 0.18786711990833282, 0.22811830043792725, 0.19436658918857574, 0.21465714275836945, 0.2115040123462677, 0.1794416755437851, 0.2146555334329605, 0.19204196333885193, 0.18770575523376465, 0.2420291155576706, 0.20038141310214996, 2.6985602378845215, 2.3520870208740234, 2.426455020904541, 1.2471671104431152, 2.042299747467041, 2.397083282470703, 1.8636339902877808, 1.5018155574798584, 2.6130876541137695, 3.0168724060058594, 2.119053840637207, 2.9539220333099365, 2.7225444316864014, 2.126840829849243, 2.0833699703216553, 2.2151951789855957, 1.4823423624038696, 2.1990373134613037, 2.2601006031036377, 2.173025131225586, 2.3496201038360596, 3.034433126449585, 2.3406972885131836, 1.4828754663467407, 2.9951107501983643, 2.284994125366211, 2.7698235511779785, 2.0488665103912354, 2.4440460205078125, 2.3768467903137207, 2.201361656188965, 1.5036594867706299, 2.22959303855896, 2.0307869911193848, 1.8067156076431274, 2.0691254138946533, 1.7820532321929932, 2.5637435913085938, 2.269171714782715, 1.377172827720642, 2.2188286781311035, 1.569993257522583, 2.00285005569458, 3.1713719367980957, 2.578446626663208, 1.234095573425293, 1.857861876487732, 2.027808904647827, 1.610188603401184, 2.5167112350463867, 2.9612388610839844, 1.6475518941879272, 1.4246604442596436, 1.8131611347198486, 1.998133659362793, 2.3077547550201416, 2.3832640647888184, 1.7232500314712524, 1.7756860256195068, 1.364402413368225, 1.6963846683502197, 2.0652847290039062, 2.602346181869507, 1.332714319229126, 1.7848507165908813, 2.4093966484069824, 2.2745537757873535, 2.0446455478668213, 1.9320131540298462, 2.4018521308898926, 3.141216993331909, 2.0353755950927734, 2.481907606124878, 1.877009391784668, 2.487421989440918, 2.0455703735351562, 1.6224110126495361, 2.0658698081970215, 1.804282784461975, 1.7725967168807983, 1.849412441253662, 2.5650110244750977, 2.6482293605804443, 1.8409812450408936, 4.245288372039795, 2.2523694038391113, 2.247023344039917, 1.8581892251968384, 1.806441307067871, 2.6012327671051025, 1.6327303647994995, 1.6466467380523682, 1.6016504764556885, 1.7467894554138184, 1.8308372497558594, 2.6774280071258545, 2.2891106605529785, 2.544837474822998, 1.2210984230041504, 2.757502317428589, 2.6129655838012695, 1.6304653882980347, 3.159271717071533, 2.2469825744628906, 2.7805442810058594, 2.048874855041504, 2.694878101348877, 2.105628728866577, 1.6390318870544434, 1.8709169626235962, 2.511472225189209, 2.3185184001922607, 2.1884067058563232, 3.051060914993286, 2.346240282058716, 1.963110327720642, 1.5272921323776245, 2.663623571395874, 2.4072673320770264, 1.4985259771347046, 2.0430455207824707, 2.738645553588867, 2.2592501640319824, 1.9534026384353638, 2.0895988941192627, 2.3715176582336426, 3.0327088832855225, 1.8899891376495361, 2.602098226547241, 2.248765707015991, 1.6159517765045166, 2.607719898223877, 2.1371567249298096, 2.1160802841186523, 3.053638219833374, 1.9937177896499634, 2.107473373413086, 2.3453426361083984, 1.7841506004333496, 2.039354085922241, 3.0958309173583984, 2.533891201019287, 1.9688142538070679, 1.5560106039047241, 1.7931526899337769, 2.133531332015991, 1.444448471069336, 2.445537567138672, 2.799487829208374, 2.5983550548553467, 3.0219547748565674, 2.4788923263549805, 2.2339673042297363, 1.763994812965393, 3.169816255569458, 2.7544643878936768, 2.715782642364502, 2.3887851238250732, 1.695842981338501, 2.594717264175415, 1.490867018699646, 2.0006113052368164, 2.690727710723877, 1.5957603454589844, 3.6477062702178955, 2.800774097442627, 1.5878698825836182, 1.8257856369018555, 1.889617919921875, 1.5983250141143799, 1.9445174932479858, 2.1653974056243896, 1.639455795288086, 1.2903344631195068, 1.6017671823501587, 2.0592362880706787, 1.030922770500183, 2.0094597339630127, 2.1620564460754395, 1.3081424236297607, 1.7998013496398926, 2.871659994125366, 1.4860210418701172, 2.349475622177124, 2.4526753425598145, 1.6360249519348145, 1.8674570322036743, 1.2613871097564697, 2.6976547241210938, 2.6061620712280273, 2.9991977214813232, 1.6516262292861938, 2.5659477710723877, 1.497356653213501, 2.0459113121032715, 2.196909189224243, 2.1635570526123047, 1.9769750833511353, 2.2813539505004883, 1.6235694885253906, 1.7478033304214478, 1.6920751333236694, 2.1822257041931152, 2.0489494800567627, 2.3633079528808594, 1.8609371185302734, 3.6395652294158936, 2.089993953704834, 2.9299874305725098, 2.934544086456299, 1.318764567375183, 1.5728851556777954, 2.030996561050415, 2.011277914047241, 1.5270769596099854, 1.4865795373916626, 1.6926788091659546, 2.438784122467041, 2.013331651687622, 1.7514005899429321, 1.3923908472061157, 2.176578998565674, 2.21890926361084, 2.703217029571533, 2.2618157863616943, 1.8289791345596313, 1.5219001770019531, 2.6986045837402344, 2.362384796142578, 1.3647454977035522, 1.7974439859390259, 1.9970060586929321, 2.792285203933716, 1.8615813255310059, 2.4159507751464844, 3.2145867347717285, 1.8524351119995117, 2.1292152404785156, 2.0712080001831055, 1.8249987363815308, 2.378068685531616, 2.6014227867126465, 1.7606451511383057, 3.491231918334961, 2.332547187805176, 2.7971324920654297, 2.391000509262085, 2.7780139446258545, 2.356734275817871, 1.8705822229385376, 2.270038366317749, 2.107874870300293, 2.5477685928344727, 3.2833333015441895, 2.0805211067199707, 2.231355905532837, 1.890795350074768, 1.8678832054138184, 2.5420989990234375, 1.7005621194839478, 2.228769540786743, 1.4977216720581055, 1.6769682168960571, 1.524173378944397, 3.143663167953491, 1.9348112344741821, 3.3574705123901367, 1.4670870304107666, 2.9920239448547363, 3.2269909381866455, 1.740354061126709, 2.2749438285827637, 2.7126822471618652, 2.4553768634796143, 2.1303300857543945, 2.3872599601745605, 2.181821346282959, 2.127716064453125, 2.4594130516052246, 2.1347672939300537, 1.6566810607910156, 2.7278366088867188, 3.328192949295044, 2.7872440814971924, 2.9768478870391846, 1.4834496974945068, 3.450106143951416, 1.7853777408599854, 1.3348678350448608, 1.6569744348526, 3.084826707839966, 1.5447111129760742, 2.6309611797332764, 2.562087297439575, 1.8727068901062012, 1.9271029233932495, 1.4703890085220337, 2.0034730434417725, 1.864428997039795, 1.9547796249389648, 93.2330093383789, 78.01841735839844, 120.7005615234375, 119.5585708618164, 204.0830078125, 83.03289794921875, 43.615116119384766, 141.2757110595703, 231.75804138183594, 87.62310028076172, 151.17169189453125, 241.4345703125, 64.32386779785156, 236.04718017578125, 250.93206787109375, 167.2287139892578, 54.956111907958984, 374.9631042480469, 256.2043151855469, 357.7115783691406, 320.34912109375, 74.11157989501953, 192.7796630859375, 166.27279663085938, 144.05746459960938, 209.6879425048828, 182.1017608642578, 150.5325927734375, 80.64241027832031, 299.7615966796875, 277.0805358886719, 96.84364318847656, 28.166872024536133, 103.3779296875, 137.70932006835938, 218.94354248046875, 335.15203857421875, 231.58642578125, 81.4869384765625, 292.12506103515625, 344.72552490234375, 33.186222076416016, 191.53675842285156, 248.1685333251953, 201.8968505859375, 178.7328643798828, 44.09561538696289, 406.694091796875, 73.12158203125, 327.26104736328125, 175.3230438232422, 84.3192138671875, 88.87325286865234, 203.2013702392578, 371.311279296875, 183.88783264160156, 53.83978271484375, 84.77294921875, 161.74815368652344, 260.4021301269531, 146.333740234375, 255.3578643798828, 99.6400146484375, 42.50799560546875, 112.7904052734375, 70.06226348876953, 127.07269287109375, 91.06526947021484, 187.70651245117188, 128.87677001953125, 42.14145278930664, 191.24020385742188, 103.27275848388672, 312.7344970703125, 97.00234985351562, 58.84244155883789, 78.07583618164062, 230.3187713623047, 43.27766036987305, 97.30560302734375, 43.7664794921875, 81.84075927734375, 233.2177276611328, 204.94168090820312, 32.1019287109375, 250.55245971679688, 102.5091552734375, 100.91826629638672, 81.4429931640625, 236.1421661376953, 76.9425048828125, 70.3829345703125, 180.445068359375, 69.59219360351562, 80.9075698852539, 219.73944091796875, 297.0400085449219, 214.1243896484375, 50.21101379394531, 50.430076599121094, 140.677978515625, 87.19078063964844, 331.50592041015625, 110.696044921875, 230.89024353027344, 99.358642578125, 154.390869140625, 170.0252685546875, 249.90061950683594, 72.85797119140625, 34.00531005859375, 373.11859130859375, 106.29347229003906, 163.856201171875, 172.78001403808594, 261.38092041015625, 194.84710693359375, 67.2374267578125, 121.4930419921875, 331.2591247558594, 139.24732971191406, 161.25006103515625, 491.15130615234375, 310.787109375, 331.5406188964844, 118.18120574951172, 91.87699890136719, 179.9495086669922, 378.1993713378906, 56.23725509643555, 70.9385757446289, 150.92605590820312, 96.21142578125, 152.28842163085938, 141.08172607421875, 67.31771087646484, 94.7668228149414, 194.8054656982422, 37.523563385009766, 47.8406982421875, 111.00349426269531, 148.05519104003906, 51.91253662109375, 184.9406280517578, 254.8236083984375, 85.53038787841797, 79.94538116455078, 66.9007568359375, 94.44207763671875, 193.39111328125, 155.95648193359375, 248.3451385498047, 113.833740234375, 210.1856231689453, 67.14106750488281, 142.99468994140625, 312.77978515625, 38.509525299072266, 79.93057250976562, 207.10888671875, 195.0006561279297, 43.34162139892578, 37.417724609375, 239.69775390625, 81.76396942138672, 135.8871307373047, 115.05156707763672, 306.8485107421875, 272.06103515625, 120.0931625366211, 152.1167755126953, 166.8426513671875, 173.9368896484375, 231.79083251953125, 72.41907501220703, 98.91802215576172, 184.7108612060547, 36.883026123046875, 52.162166595458984, 113.22091674804688, 160.7015838623047, 177.1009521484375, 46.310760498046875, 335.3111572265625, 74.63333129882812, 187.14866638183594, 83.25733184814453, 247.47021484375, 64.63311004638672, 198.53819274902344, 37.4976806640625, 151.1491241455078, 120.3856201171875, 292.8326416015625, 44.267948150634766, 238.22378540039062, 56.396541595458984, 146.38421630859375, 76.25001525878906, 127.734130859375, 413.1126708984375, 281.440185546875, 152.99794006347656, 286.6701965332031, 626.453369140625, 74.97560119628906, 95.45355224609375, 140.50355529785156, 329.6334228515625, 213.0071563720703, 52.410316467285156, 49.45869064331055, 57.336395263671875, 277.6493225097656, 244.2236328125, 111.86894989013672, 348.28375244140625, 82.68534851074219, 66.27812957763672, 133.66822814941406, 234.71121215820312, 172.3100128173828, 71.34966278076172, 117.18091583251953, 43.5518798828125, 114.52140045166016, 62.619384765625, 337.7449035644531, 201.34593200683594, 183.9181671142578, 177.52061462402344, 78.2558364868164, 179.4840545654297, 191.19384765625, 417.046875, 219.953125, 185.2908477783203, 147.8133544921875, 39.306365966796875, 165.53585815429688, 191.72998046875, 40.96442413330078, 117.31914520263672, 153.09674072265625, 116.56938934326172, 300.8063049316406, 160.83287048339844, 179.3953399658203, 64.0950927734375, 188.2117919921875, 185.493896484375, 236.257568359375, 28.621826171875, 133.46185302734375, 302.013427734375, 145.35305786132812, 221.983154296875, 170.927734375, 200.8076934814453, 91.06278228759766, 50.851287841796875, 149.36351013183594, 265.69635009765625, 155.3947296142578, 51.96344757080078, 139.28941345214844, 111.74935150146484, 140.010498046875, 114.12186431884766, 440.2238464355469, 300.26910400390625, 162.90548706054688, 62.95640182495117, 66.40402221679688, 266.78057861328125, 149.66290283203125, 276.81219482421875, 299.142578125, 373.7830505371094, 229.98585510253906, 92.03960418701172, 99.3624038696289, 101.90936279296875, 160.44882202148438, 64.9549560546875, 88.364501953125, 40.79254150390625, 285.9314270019531, 91.63361358642578, 135.7453155517578, 276.83258056640625, 424.4581604003906, 95.127197265625, 260.1549072265625, 254.99609375, 187.70140075683594, 196.3671875, 41.70361328125, 50.39888381958008, 118.16666412353516, 2.100708246231079, 2.331936836242676, 2.703580379486084, 2.1532697677612305, 2.577305793762207, 2.5133447647094727, 3.068619966506958, 1.4560614824295044, 2.800776243209839, 1.8556567430496216, 2.0628767013549805, 3.7675769329071045, 2.6183764934539795, 2.6771633625030518, 1.9824038743972778, 2.1837282180786133, 4.16007661819458, 3.610386848449707, 3.0886988639831543, 3.04439640045166, 1.4633666276931763, 2.50919508934021, 3.181011915206909, 2.6043996810913086, 3.4690067768096924, 3.1345601081848145, 1.4998315572738647, 1.9723252058029175, 1.9707937240600586, 2.932236909866333, 0.9785366654396057, 1.543418288230896, 3.611353635787964, 2.529883861541748, 2.5281894207000732, 2.5253467559814453, 3.0683000087738037, 1.7543615102767944, 3.373828411102295, 2.3575222492218018, 4.235537528991699, 2.787055015563965, 2.9220306873321533, 1.772353172302246, 3.7026188373565674, 3.16499924659729, 1.9335427284240723, 2.04245662689209, 3.1673991680145264, 1.752272605895996, 3.0380890369415283, 2.352109670639038, 2.8165788650512695, 3.324817657470703, 2.5544674396514893, 2.922147035598755, 2.023411750793457, 2.653986692428589, 3.20924973487854, 2.77609920501709, 2.883742570877075, 2.57564640045166, 2.2938644886016846, 2.128164052963257, 3.3373708724975586, 2.2336864471435547, 3.317835569381714, 3.0284111499786377, 1.718292236328125, 1.8281525373458862, 2.2935616970062256, 2.1681764125823975, 1.8938246965408325, 2.0411369800567627, 2.440626859664917, 2.477118492126465, 2.7107062339782715, 2.570754289627075, 2.5754494667053223, 2.8992321491241455, 2.079965591430664, 2.382798194885254, 3.0290210247039795, 1.941884160041809, 1.2877771854400635, 2.539393424987793, 2.646540403366089, 2.327777862548828, 3.21335506439209, 3.589637041091919, 3.050445556640625, 3.624953508377075, 1.9143673181533813, 2.7956743240356445, 1.632271647453308, 2.2824182510375977, 1.9004813432693481, 2.8749923706054688, 2.1375741958618164, 2.715399980545044, 3.4984447956085205, 2.3973629474639893, 2.442950487136841, 2.5341806411743164, 2.405817747116089, 2.7233593463897705, 3.017789125442505, 3.672053813934326, 3.2800819873809814, 2.4454965591430664, 3.1304850578308105, 3.6782023906707764, 1.4824094772338867, 2.7557713985443115, 4.1321940422058105, 3.559220552444458, 2.4953207969665527, 2.0243024826049805, 2.9282047748565674, 1.8717858791351318, 1.4582555294036865, 2.7254152297973633, 2.032803535461426, 2.4444360733032227, 1.6411516666412354, 2.592097043991089, 1.577618956565857, 2.7424097061157227, 2.8052666187286377, 2.832597017288208, 3.1849467754364014, 3.996066093444824, 2.3917009830474854, 2.3518435955047607, 1.74315345287323, 3.4505107402801514, 2.213059425354004, 2.138871669769287, 3.175734281539917, 4.153926372528076, 2.2747700214385986, 2.397406578063965, 2.8944737911224365, 1.6811785697937012, 2.3904294967651367, 2.395413875579834, 1.7061004638671875, 1.9951027631759644, 2.1055121421813965, 2.3549821376800537, 2.439532518386841, 3.124166488647461, 1.8711507320404053, 2.89453125, 2.931288957595825, 2.4553022384643555, 3.247267484664917, 1.7217172384262085, 1.48481285572052, 3.3461174964904785, 3.068585157394409, 2.002070426940918, 3.2919797897338867, 3.2224693298339844, 2.147109031677246, 1.761281132698059, 3.5346899032592773, 1.4256582260131836, 3.039689302444458, 1.506733775138855, 2.97067928314209, 3.050543785095215, 3.0429179668426514, 2.9703874588012695, 2.8890106678009033, 2.8621490001678467, 2.215773582458496, 2.862330913543701, 2.703373908996582, 3.2326841354370117, 2.231379508972168, 2.4717109203338623, 2.0989415645599365, 2.5933330059051514, 1.4960699081420898, 2.6559078693389893, 2.525975227355957, 3.4499194622039795, 2.054154396057129, 2.1406869888305664, 2.7938740253448486, 3.3339414596557617, 2.5849030017852783, 2.0513317584991455, 1.9643560647964478, 2.082934856414795, 1.6811959743499756, 3.62668514251709, 2.1908884048461914, 2.3792290687561035, 2.9403743743896484, 2.510025978088379, 2.4669156074523926, 2.485232353210449, 3.088529586791992, 1.6648186445236206, 1.6811953783035278, 3.7836997509002686, 2.0135085582733154, 3.5784823894500732, 2.816739320755005, 1.7223844528198242, 2.877877950668335, 2.597028970718384, 3.284205198287964, 4.087613582611084, 2.2722582817077637, 2.561908006668091, 2.2134029865264893, 2.4941961765289307, 2.399460792541504, 2.2491042613983154, 2.321394205093384, 2.7759032249450684, 3.5488157272338867, 2.017289876937866, 3.3603672981262207, 1.7163366079330444, 3.9347493648529053, 1.9903974533081055, 2.9742138385772705, 1.7278738021850586, 3.325820207595825, 2.3387258052825928, 2.889569044113159, 2.840806245803833, 2.8333165645599365, 1.7885674238204956, 2.7761759757995605, 3.052722454071045, 1.7947783470153809, 2.5324506759643555, 2.484708309173584, 2.8705456256866455, 2.3400912284851074, 2.6722424030303955, 2.4317760467529297, 2.971234083175659, 3.4619438648223877, 2.081855535507202, 3.1942694187164307, 2.3017797470092773, 1.9718962907791138, 3.316197395324707, 3.497037887573242, 2.084125518798828, 2.3110547065734863, 3.390059232711792, 1.2238013744354248, 2.5847830772399902, 4.2262678146362305, 1.884371042251587, 3.5428738594055176, 2.0590977668762207, 2.5288264751434326, 3.484025239944458, 1.8260010480880737, 2.708453416824341, 1.597493052482605, 2.2225074768066406, 2.549429178237915, 3.2513885498046875, 2.8466904163360596, 2.00788950920105, 1.7882685661315918, 4.046032905578613, 3.0289623737335205, 2.2006444931030273, 2.3120245933532715, 2.7080705165863037, 2.788569927215576, 1.7022662162780762, 2.2401247024536133, 2.4250574111938477, 3.8246006965637207, 2.5162429809570312, 3.073216438293457, 2.2886459827423096, 2.937182664871216, 2.065124988555908, 1.8499881029129028, 2.6201722621917725, 2.649205207824707, 3.195584535598755, 3.234527587890625, 3.2525341510772705, 1.7259461879730225, 2.6765947341918945, 3.1078271865844727, 3.235356330871582, 0.23261530697345734, 0.1653883308172226, 0.20418591797351837, 0.189671128988266, 0.13692784309387207, 0.19283610582351685, 0.231012225151062, 0.27884605526924133, 0.233804851770401, 0.16314101219177246, 0.2640630304813385, 0.11939022690057755, 0.2165212631225586, 0.2102232575416565, 0.21106964349746704, 0.16880133748054504, 0.2477160394191742, 0.15103663504123688, 0.14027085900306702, 0.2195553481578827, 0.18106436729431152, 0.18708041310310364, 0.23205533623695374, 0.1836542785167694, 0.14749853312969208, 0.18744297325611115, 0.1956876963376999, 0.2698836028575897, 0.2690736651420593, 0.2547416388988495, 0.1726195067167282, 0.1785700023174286, 0.234686940908432, 0.23013423383235931, 0.2485467791557312, 0.2296157330274582, 0.22102351486682892, 0.19260497391223907, 0.2496263086795807, 0.18841977417469025, 0.20698247849941254, 0.22910521924495697, 0.16046646237373352, 0.1848960667848587, 0.21971091628074646, 0.21323463320732117, 0.18691280484199524, 0.18680833280086517, 0.17952701449394226, 0.17077139019966125, 0.1884017288684845, 0.25185343623161316, 0.1996031403541565, 0.2236097902059555, 0.18996527791023254, 0.16605904698371887, 0.20038795471191406, 0.14283059537410736, 0.16065165400505066, 0.25756174325942993, 0.16396686434745789, 0.12440408766269684, 0.23086297512054443, 0.20030827820301056, 0.1776391565799713, 0.21082448959350586, 0.19963438808918, 0.21308588981628418, 0.17039118707180023, 0.1913578063249588, 0.2918027341365814, 0.2314797192811966, 0.27099016308784485, 0.2777668833732605, 0.24153488874435425, 0.21101614832878113, 0.2552712559700012, 0.2692042887210846, 0.20520861446857452, 0.16184943914413452, 0.19380569458007812, 0.1526615172624588, 0.18353892862796783, 0.21751153469085693, 0.20119185745716095, 0.1797085553407669, 0.29299724102020264, 0.24171021580696106, 0.26492705941200256, 0.3170071244239807, 0.25393790006637573, 0.23040398955345154, 0.2612878978252411, 0.2243286520242691, 0.22036901116371155, 0.24133765697479248, 0.1907636970281601, 0.29893770813941956, 0.15014740824699402, 0.24892571568489075, 0.20106585323810577, 0.20957519114017487, 0.23710258305072784, 0.20365183055400848, 0.1767580211162567, 0.17150746285915375, 0.24128039181232452, 0.2411041557788849, 0.23912642896175385, 0.2834697961807251, 0.2567306160926819, 0.1748851090669632, 0.13322167098522186, 0.23120997846126556, 0.22190482914447784, 0.22510406374931335, 0.22554855048656464, 0.24492301046848297, 0.19461090862751007, 0.15095849335193634, 0.1919952780008316, 0.18870438635349274, 0.20802848041057587, 0.2100360244512558, 0.1667533665895462, 0.2551264762878418, 0.23711752891540527, 0.19041544198989868, 0.1991979330778122, 0.2396712601184845, 0.27418917417526245, 0.2172221690416336, 0.22398017346858978, 0.23338660597801208, 0.1840987354516983, 0.17775081098079681, 0.19372646510601044, 0.1820427030324936, 0.2003006935119629, 0.2614371180534363, 0.18516936898231506, 0.2368815541267395, 0.1625104546546936, 0.11553124338388443, 0.2203170657157898, 0.13501377403736115, 0.289416640996933, 0.2366728037595749, 0.23353427648544312, 0.19621184468269348, 0.18888415396213531, 0.2356034368276596, 0.23354238271713257, 0.22337815165519714, 0.23960447311401367, 0.24483071267604828, 0.23701171576976776, 0.19147929549217224, 0.15615934133529663, 0.2591298222541809, 0.2480238676071167, 0.22009074687957764, 0.18932875990867615, 0.2860812842845917, 0.2693849802017212, 0.20636878907680511, 0.22689270973205566, 0.22407276928424835, 0.22565801441669464, 0.23380205035209656, 0.30527570843696594, 0.24446319043636322, 0.16627754271030426, 0.20666739344596863, 0.24830229580402374, 0.30004894733428955, 0.18349578976631165, 0.2358148843050003, 0.1763768494129181, 0.18041378259658813, 0.23977412283420563, 0.22718429565429688, 0.18241877853870392, 0.24789351224899292, 0.24619875848293304, 0.2062535434961319, 0.22054162621498108, 0.22040922939777374, 0.19224461913108826, 0.1596672236919403, 0.26270994544029236, 0.1831389218568802, 0.1929740309715271, 0.20401786267757416, 0.23821696639060974, 0.1861252337694168, 0.2031748741865158, 0.22715957462787628, 0.24305564165115356, 0.21435028314590454, 0.23560135066509247, 0.19721318781375885, 0.13794495165348053, 0.17512629926204681, 0.18673735857009888, 0.24657028913497925, 0.17358767986297607, 0.28528785705566406, 0.17744460701942444, 0.19874194264411926, 0.19144107401371002, 0.18802578747272491, 0.18879388272762299, 0.3062051236629486, 0.21623492240905762, 0.15408514440059662, 0.22441023588180542, 0.1820967048406601, 0.17689673602581024, 0.20017936825752258, 0.19850952923297882, 0.26690733432769775, 0.15442104637622833, 0.19258174300193787, 0.24048151075839996, 0.2523294687271118, 0.20053422451019287, 0.1760019063949585, 0.273537814617157, 0.23377609252929688, 0.22686420381069183, 0.23580209910869598, 0.20936179161071777, 0.14517024159431458, 0.2339312732219696, 0.2318570613861084, 0.2624431252479553, 0.20819850265979767, 0.21887455880641937, 0.20993392169475555, 0.3210177421569824, 0.1774444878101349, 0.2635701596736908, 0.15706861019134521, 0.21751663088798523, 0.23004280030727386, 0.20482784509658813, 0.17361249029636383, 0.24786365032196045, 0.23196318745613098, 0.21979792416095734, 0.24213089048862457, 0.22349025309085846, 0.19718913733959198, 0.23324401676654816, 0.1927318125963211, 0.2224515825510025, 0.18195828795433044, 0.1989508718252182, 0.22467811405658722, 0.20692947506904602, 0.1947169005870819, 0.22467021644115448, 0.19910494983196259, 0.25592103600502014, 0.26268863677978516, 0.20814870297908783, 0.20317555963993073, 0.1980893611907959, 0.2050924003124237, 0.15802767872810364, 0.26994457840919495, 0.241891011595726, 0.22670836746692657, 0.21512556076049805, 0.15498241782188416, 0.1821473389863968, 0.2902233302593231, 0.24917833507061005, 0.2512616217136383, 0.23069922626018524, 0.21403396129608154, 0.15396541357040405, 0.12148889154195786, 0.18531079590320587, 0.19750308990478516, 0.26895463466644287, 0.18686604499816895, 0.25087106227874756, 0.19336029887199402, 0.21793468296527863, 0.21543945372104645, 0.26923879981040955, 0.21830129623413086, 0.25912004709243774, 0.28821587562561035, 0.16265520453453064, 0.22347623109817505, 0.2279067486524582, 0.30668994784355164, 2.3495123386383057, 1.8767238855361938, 2.2452383041381836, 2.591949939727783, 3.298004627227783, 3.121246337890625, 1.9538275003433228, 2.3309950828552246, 2.0098135471343994, 2.9282894134521484, 2.0668258666992188, 1.988986611366272, 2.2686922550201416, 2.09713077545166, 1.803880214691162, 1.913454294204712, 1.988893985748291, 1.6693300008773804, 2.3353030681610107, 2.2304043769836426, 1.4797815084457397, 2.4461026191711426, 1.7097479104995728, 3.0537209510803223, 2.090998649597168, 3.2231674194335938, 1.9729845523834229, 2.5016446113586426, 1.2177480459213257, 1.6483434438705444, 1.9364190101623535, 2.2495856285095215, 2.1224400997161865, 2.0255184173583984, 2.7315704822540283, 2.191959857940674, 3.045151948928833, 2.268500328063965, 2.499436378479004, 1.9533075094223022, 2.3430402278900146, 1.811271071434021, 2.3862853050231934, 2.1897432804107666, 2.9032344818115234, 1.383315086364746, 1.8558648824691772, 2.429870128631592, 2.1463370323181152, 2.099672555923462, 2.1433773040771484, 2.4624321460723877, 2.5697076320648193, 2.0322256088256836, 1.2227191925048828, 1.8174656629562378, 1.7720600366592407, 1.923198938369751, 2.398699998855591, 1.9519071578979492, 1.2779467105865479, 2.326270341873169, 2.2461726665496826, 2.3720998764038086, 3.566289186477661, 2.7457215785980225, 2.1142897605895996, 2.8763396739959717, 3.056628465652466, 2.4884653091430664, 2.8743908405303955, 2.0141420364379883, 1.6834124326705933, 1.7757821083068848, 1.0972800254821777, 2.124958038330078, 2.144666910171509, 1.923054575920105, 2.1604971885681152, 3.0792553424835205, 2.3206889629364014, 1.8797067403793335, 1.6701933145523071, 1.3738726377487183, 2.1972262859344482, 2.1231322288513184, 1.8504180908203125, 1.9182583093643188, 4.047778606414795, 2.276064157485962, 2.294912576675415, 1.8648912906646729, 2.7507781982421875, 1.9812291860580444, 1.79351806640625, 2.2399039268493652, 2.2818222045898438, 2.7578399181365967, 2.6863391399383545, 2.231635570526123, 1.50394868850708, 2.0708889961242676, 2.351022481918335, 2.297914743423462, 2.6420342922210693, 2.366968870162964, 1.8063368797302246, 1.5286611318588257, 1.6845133304595947, 1.97179114818573, 2.358376979827881, 1.5215922594070435, 2.009982109069824, 1.3118627071380615, 1.6100695133209229, 2.028381824493408, 1.754638910293579, 2.447899341583252, 1.719136118888855, 3.1265182495117188, 4.1390252113342285, 1.5402648448944092, 1.9438637495040894, 1.8103469610214233, 1.9922773838043213, 1.2363158464431763, 1.5819180011749268, 1.82498037815094, 2.9217960834503174, 2.350010871887207, 2.6281304359436035, 3.080329179763794, 2.7137608528137207, 1.4593029022216797, 2.0059289932250977, 2.3729453086853027, 2.114248275756836, 1.3675689697265625, 2.0296809673309326, 2.3489489555358887, 2.9934868812561035, 1.4442535638809204, 1.7870292663574219, 1.9365371465682983, 1.7857455015182495, 2.4198379516601562, 2.0698578357696533, 1.5112195014953613, 2.318129301071167, 2.145702838897705, 2.082967758178711, 1.9483087062835693, 2.010697603225708, 2.774385929107666, 2.06616473197937, 2.7683327198028564, 3.0091753005981445, 3.1196630001068115, 2.003316640853882, 1.4310226440429688, 1.6256166696548462, 2.293609857559204, 1.8046766519546509, 2.436041831970215, 2.518911600112915, 2.3576128482818604, 1.1600556373596191, 1.6709628105163574, 2.023637294769287, 1.5163347721099854, 1.5646412372589111, 1.712188720703125, 1.9093941450119019, 1.9052196741104126, 1.9601742029190063, 2.44210147857666, 2.9046406745910645, 2.223264217376709, 2.0661041736602783, 2.3864858150482178, 2.5320897102355957, 1.8635250329971313, 2.402799606323242, 1.7923176288604736, 2.456479549407959, 2.363415241241455, 3.253687620162964, 2.8330330848693848, 1.7637684345245361, 1.6437307596206665, 3.0226781368255615, 2.3413214683532715, 1.7250847816467285, 1.6920884847640991, 2.0864524841308594, 3.0314559936523438, 2.4123780727386475, 1.333626389503479, 1.8464494943618774, 1.6276606321334839, 1.978441834449768, 1.4419938325881958, 2.528461456298828, 1.6504625082015991, 1.8850417137145996, 2.637449264526367, 1.942991018295288, 2.5923967361450195, 2.1473629474639893, 2.271087408065796, 2.2414846420288086, 2.1393203735351562, 1.8374252319335938, 2.721268892288208, 2.0762624740600586, 1.6042046546936035, 2.1600704193115234, 1.870730996131897, 2.4437286853790283, 1.7696783542633057, 1.30913245677948, 2.2888665199279785, 2.695208787918091, 2.191301107406616, 2.056461811065674, 2.1896257400512695, 3.155371904373169, 2.4611611366271973, 1.8980486392974854, 4.000605583190918, 2.2946343421936035, 2.2814416885375977, 1.5522249937057495, 1.6939817667007446, 2.863959550857544, 2.287740468978882, 1.7410577535629272, 2.4930458068847656, 1.3891607522964478, 2.8062660694122314, 2.363994598388672, 2.695681095123291, 2.0236008167266846, 2.4447436332702637, 2.821991443634033, 1.351015329360962, 2.564398765563965, 2.6961429119110107, 2.4605250358581543, 2.0649542808532715, 2.4376890659332275, 2.9022586345672607, 2.777844190597534, 2.317772388458252, 1.331781268119812, 2.390596628189087, 1.7772935628890991, 3.3293492794036865, 1.9940557479858398, 1.8437285423278809, 2.1129417419433594, 3.0634567737579346, 2.4448297023773193, 2.202681303024292, 2.793097734451294, 2.333606004714966, 1.9532561302185059, 2.2879691123962402, 1.8256163597106934, 2.8843657970428467, 2.152545690536499, 2.3916783332824707, 2.6700439453125, 1.4616198539733887, 1.810018539428711, 1.6819521188735962, 1.5989919900894165, 1.4934583902359009, 1.8981280326843262, 1.9340696334838867, 2.388442039489746, 1.9259248971939087, 2.225925922393799, 3.0143959522247314, 1.7467913627624512, 2.0986790657043457, 2.1468324661254883, 2.1314430236816406, 2.556762218475342, 3.020958423614502, 1.6344105005264282, 1.98689603805542, 2.6626458168029785, 1.5770952701568604, 2.6002533435821533, 2.3182425498962402, 2.90586256980896, 2.2181758880615234, 2.257267951965332, 1.7755762338638306, 61.9771728515625, 177.65101623535156, 179.92062377929688, 147.08477783203125, 103.8572998046875, 174.2320098876953, 147.78135681152344, 137.63656616210938, 139.36734008789062, 312.0551452636719, 342.72039794921875, 71.57513427734375, 167.35464477539062, 66.4578857421875, 90.77933502197266, 159.49761962890625, 294.3209228515625, 63.907772064208984, 104.40975952148438, 163.9013214111328, 457.6888122558594, 35.648963928222656, 312.419921875, 63.70330810546875, 122.8092269897461, 48.30926513671875, 43.56385803222656, 168.17660522460938, 139.008056640625, 131.21136474609375, 59.42032241821289, 152.88351440429688, 113.9588623046875, 53.856258392333984, 87.06396484375, 126.23504638671875, 295.3908386230469, 82.03597259521484, 113.02962493896484, 271.599609375, 47.557254791259766, 227.15625, 304.7962341308594, 88.77935028076172, 46.785945892333984, 185.41270446777344, 242.4144287109375, 211.68858337402344, 326.69964599609375, 52.47861099243164, 62.019287109375, 309.3419494628906, 270.9330749511719, 204.574951171875, 214.29701232910156, 97.82964324951172, 99.44429779052734, 153.15570068359375, 38.35207748413086, 279.8796081542969, 153.63580322265625, 287.2806091308594, 121.90478515625, 309.7882385253906, 103.48957824707031, 183.40042114257812, 81.01721954345703, 484.6798400878906, 140.00137329101562, 241.2431182861328, 152.04669189453125, 63.49551010131836, 128.41470336914062, 233.50927734375, 166.89306640625, 167.1111297607422, 153.9891357421875, 93.54454803466797, 159.36557006835938, 163.37950134277344, 323.03118896484375, 160.17344665527344, 235.86203002929688, 235.03370666503906, 128.24359130859375, 120.92515563964844, 108.42996978759766, 211.83799743652344, 226.1083984375, 100.2999267578125, 58.885257720947266, 145.51475524902344, 187.1671905517578, 109.19232940673828, 135.8035888671875, 40.94549560546875, 84.41390228271484, 149.92788696289062, 100.76448059082031, 320.959716796875, 54.38316345214844, 171.31651306152344, 167.05235290527344, 299.0079345703125, 198.05284118652344, 212.6511993408203, 36.223419189453125, 187.0243377685547, 35.4180908203125, 75.777587890625, 147.3141326904297, 75.98365020751953, 91.05316925048828, 207.69866943359375, 414.9123229980469, 216.5865020751953, 101.44696044921875, 192.2613067626953, 321.5191650390625, 178.3197021484375, 96.3712158203125, 440.8111877441406, 140.08470153808594, 38.98835372924805, 56.0865478515625, 93.85356903076172, 179.5536651611328, 94.86930084228516, 217.8417510986328, 225.42999267578125, 156.568603515625, 137.19659423828125, 240.552734375, 142.7521209716797, 69.02468872070312, 95.5282211303711, 169.6951904296875, 181.2801513671875, 111.67749786376953, 121.44585418701172, 132.58018493652344, 106.746337890625, 176.2948760986328, 273.1518859863281, 142.166015625, 59.5966796875, 221.65057373046875, 309.7649841308594, 142.64898681640625, 111.01678466796875, 275.0028076171875, 327.3269958496094, 229.1050567626953, 283.1600646972656, 43.516357421875, 174.9186553955078, 316.4590148925781, 349.7904357910156, 45.65095520019531, 239.3651580810547, 134.7008819580078, 314.5125732421875, 215.92913818359375, 106.599853515625, 380.8874816894531, 65.89702606201172, 218.1892852783203, 139.99984741210938, 449.7113037109375, 51.036678314208984, 61.878143310546875, 41.83522415161133, 103.87630462646484, 71.38819885253906, 80.51063537597656, 60.072998046875, 45.00531005859375, 82.91675567626953, 364.97564697265625, 36.57878875732422, 30.858049392700195, 105.9952621459961, 283.717529296875, 40.497802734375, 89.03802490234375, 224.68389892578125, 97.2977294921875, 342.382568359375, 163.2142333984375, 206.4940948486328, 267.46875, 114.48331451416016, 130.79827880859375, 113.45193481445312, 411.092529296875, 70.45976257324219, 133.18165588378906, 175.59695434570312, 104.89837646484375, 144.384033203125, 405.7861328125, 396.90576171875, 107.56046295166016, 31.61480712890625, 73.3050537109375, 133.4164276123047, 372.24810791015625, 45.843353271484375, 115.68115234375, 353.90924072265625, 466.9494323730469, 314.32379150390625, 165.64605712890625, 126.40337371826172, 345.8209228515625, 72.3580322265625, 125.84466552734375, 74.42567443847656, 113.9916000366211, 108.75125122070312, 69.411865234375, 153.47593688964844, 119.060546875, 225.2801055908203, 224.50794982910156, 115.421630859375, 224.57379150390625, 155.66567993164062, 67.2371826171875, 106.71595764160156, 196.01513671875, 199.65562438964844, 54.96014404296875, 293.86151123046875, 100.08548736572266, 171.56845092773438, 180.5047607421875, 220.126953125, 144.60272216796875, 139.32388305664062, 204.4405059814453, 149.149169921875, 143.73585510253906, 176.94541931152344, 54.95721435546875, 59.573875427246094, 93.96904754638672, 263.3419494628906, 185.9771270751953, 92.54837799072266, 35.200927734375, 55.695369720458984, 225.828125, 36.21640396118164, 142.23583984375, 154.17982482910156, 165.36663818359375, 58.1573486328125, 150.05165100097656, 177.15414428710938, 42.7186279296875, 50.23732376098633, 304.40399169921875, 109.31488037109375, 49.5781135559082, 50.37189865112305, 139.18475341796875, 96.5911865234375, 42.32422637939453, 152.92074584960938, 211.8554229736328, 131.67674255371094, 134.12335205078125, 59.68821334838867, 113.78565979003906, 55.0571174621582, 92.66385650634766, 79.39166259765625, 128.58229064941406, 290.474365234375, 166.70751953125, 269.76715087890625, 85.98849487304688, 128.0360107421875, 32.503662109375, 60.556541442871094, 165.56382751464844, 382.5589904785156, 129.2746124267578, 153.6974334716797, 38.69301986694336, 49.169246673583984, 85.7392578125, 104.06212615966797, 185.94786071777344, 188.4384765625, 223.51678466796875, 144.00502014160156, 288.0635986328125, 45.755859375, 3.0352282524108887, 1.996823787689209, 1.7437204122543335, 2.5494046211242676, 2.169508934020996, 1.639018177986145, 2.4235124588012695, 3.940070152282715, 2.3358027935028076, 1.7277251482009888, 2.236524820327759, 2.821678638458252, 2.242417335510254, 3.635531425476074, 2.6013307571411133, 1.9407806396484375, 2.529597759246826, 2.195897102355957, 3.0083606243133545, 3.7551281452178955, 2.6530163288116455, 1.1888647079467773, 2.8476827144622803, 2.598707914352417, 1.650024652481079, 2.452958106994629, 1.7132296562194824, 3.0200352668762207, 2.3221523761749268, 3.321509838104248, 2.655109167098999, 2.3384313583374023, 2.586806535720825, 1.7710528373718262, 2.7802417278289795, 2.5837719440460205, 2.0030760765075684, 2.4865927696228027, 3.6614930629730225, 2.138214588165283, 2.632190704345703, 2.5010733604431152, 2.759658098220825, 3.1216421127319336, 2.6349823474884033, 2.4895429611206055, 2.352353096008301, 2.338770627975464, 3.6017980575561523, 3.4846127033233643, 3.185575246810913, 2.9101686477661133, 2.0039169788360596, 2.0236294269561768, 1.4511040449142456, 3.7064437866210938, 2.859454870223999, 2.522805690765381, 2.6629114151000977, 2.742811918258667, 1.9864301681518555, 3.0677380561828613, 2.1708452701568604, 3.0619192123413086, 2.8098254203796387, 3.0512382984161377, 2.167281150817871, 2.7922258377075195, 2.763871431350708, 1.974027395248413, 2.3325910568237305, 2.421483039855957, 2.155095100402832, 2.299607276916504, 3.2797210216522217, 3.3684794902801514, 3.2329399585723877, 3.0007290840148926, 2.8768091201782227, 3.057706117630005, 1.9202086925506592, 1.7584404945373535, 3.588414430618286, 2.5605125427246094, 2.6925554275512695, 3.389338254928589, 2.5159637928009033, 1.8291887044906616, 2.896419048309326, 2.137387990951538, 2.380845546722412, 3.315809965133667, 2.5807793140411377, 3.2389605045318604, 2.89078426361084, 2.668881416320801, 2.150822639465332, 2.7267065048217773, 2.2275426387786865, 2.3371574878692627, 2.689115285873413, 3.0840752124786377, 1.9138669967651367, 1.60962975025177, 2.3488430976867676, 1.909859538078308, 2.862602472305298, 3.024981737136841, 1.9015051126480103, 3.383974552154541, 2.4154434204101562, 2.570835590362549, 2.5185768604278564, 1.8443325757980347, 2.7358293533325195, 3.844075918197632, 2.312311887741089, 2.301854133605957, 1.934831976890564, 2.455683469772339, 3.321645736694336, 3.6025030612945557, 2.3825130462646484, 2.6694629192352295, 3.4261999130249023, 2.4240219593048096, 2.8737785816192627, 2.659165620803833, 2.737225294113159, 2.798154830932617, 3.1878154277801514, 3.0494463443756104, 3.207209348678589, 2.291733741760254, 3.1040563583374023, 1.6905851364135742, 2.146047830581665, 3.3433926105499268, 1.9026840925216675, 3.6128015518188477, 1.9347954988479614, 3.421666145324707, 3.4879026412963867, 2.54268217086792, 2.860069751739502, 1.6498597860336304, 2.2674615383148193, 3.415154457092285, 2.7492306232452393, 2.684321641921997, 3.58028244972229, 2.1767990589141846, 4.196352005004883, 1.3967397212982178, 2.8254079818725586, 4.407893180847168, 1.8058881759643555, 2.2118406295776367, 3.0670104026794434, 2.0299787521362305, 2.084644317626953, 1.784127116203308, 2.3902599811553955, 2.8419477939605713, 2.849318265914917, 2.729506492614746, 3.2652904987335205, 1.770400047302246, 2.916491746902466, 2.229430913925171, 1.3941683769226074, 3.2438268661499023, 1.8040777444839478, 2.2292776107788086, 1.8490362167358398, 2.687971830368042, 2.4416818618774414, 4.343627452850342, 2.7253963947296143, 2.9764697551727295, 1.8389214277267456, 3.315882444381714, 2.1751718521118164, 1.633786916732788, 2.2689619064331055, 2.836394786834717, 2.9136979579925537, 3.5637762546539307, 2.030644416809082, 2.128342628479004, 3.530928373336792, 1.5086262226104736, 2.0704739093780518, 1.8868060111999512, 1.5095571279525757, 4.264732360839844, 2.9309167861938477, 2.6603732109069824, 3.7026078701019287, 3.323533296585083, 1.7758272886276245, 1.944356083869934, 1.606781005859375, 1.904372215270996, 3.277891159057617, 2.213311195373535, 2.515904426574707, 2.777087450027466, 3.156907320022583, 2.4304590225219727, 2.489734649658203, 2.0634562969207764, 2.374363660812378, 2.162949562072754, 1.782543420791626, 2.6636862754821777, 3.150272846221924, 2.3606925010681152, 2.5200035572052, 3.0821986198425293, 2.1115517616271973, 4.068894386291504, 2.448502540588379, 3.098238468170166, 1.4450352191925049, 3.070990562438965, 1.8393964767456055, 2.619216203689575, 3.5454516410827637, 3.164008140563965, 3.1131646633148193, 1.630783200263977, 2.17954683303833, 1.8338745832443237, 3.6553356647491455, 3.0557167530059814, 2.2426555156707764, 2.6970982551574707, 2.5925111770629883, 2.265334129333496, 3.0849733352661133, 2.0776758193969727, 3.2128796577453613, 2.7225852012634277, 2.690080165863037, 2.6470673084259033, 2.3465261459350586, 3.063183546066284, 3.3610546588897705, 2.0245752334594727, 1.9019707441329956, 2.115556001663208, 3.574772834777832, 2.5322279930114746, 1.8838485479354858, 2.5032358169555664, 3.679701566696167, 2.520375967025757, 2.0177578926086426, 2.609675884246826, 1.754626750946045, 2.2178432941436768, 2.35311222076416, 1.9520940780639648, 2.250798225402832, 3.3218910694122314, 2.471991539001465, 3.4902501106262207, 2.183415412902832, 2.887219190597534, 1.854636311531067, 3.451874256134033, 3.5796384811401367, 2.3827428817749023, 2.1018574237823486, 2.0426881313323975, 2.8882253170013428, 2.2394931316375732, 2.716378927230835, 3.34561824798584, 1.8474035263061523, 3.842709541320801, 3.4365556240081787, 2.213418483734131, 3.765160083770752, 3.9055233001708984, 2.887125253677368, 2.8044962882995605, 2.719435930252075, 1.7304390668869019, 2.4645586013793945, 2.504063606262207, 1.7314703464508057, 2.667393684387207, 3.816307783126831, 3.3421757221221924, 2.2412424087524414, 1.61400306224823, 4.5846333503723145, 3.1579906940460205, 0.18065081536769867, 0.20497046411037445, 0.2099081426858902, 0.2778116762638092, 0.2352478951215744, 0.22745072841644287, 0.2831818759441376, 0.26147228479385376, 0.22879016399383545, 0.20549258589744568, 0.21531713008880615, 0.22670142352581024, 0.1948198825120926, 0.20960766077041626, 0.22722205519676208, 0.21177393198013306, 0.2702460289001465, 0.15735110640525818, 0.3343033492565155, 0.2031536102294922, 0.24714834988117218, 0.21914148330688477, 0.19037014245986938, 0.2032558023929596, 0.25781702995300293, 0.24177272617816925, 0.24796895682811737, 0.18901322782039642, 0.20525074005126953, 0.22477179765701294, 0.22606529295444489, 0.19269461929798126, 0.1958456188440323, 0.17728538811206818, 0.19998417794704437, 0.2294348031282425, 0.19639818370342255, 0.21902234852313995, 0.14973148703575134, 0.19214747846126556, 0.2380496859550476, 0.20567291975021362, 0.218236044049263, 0.2461983561515808, 0.20819933712482452, 0.18488706648349762, 0.17992572486400604, 0.22253820300102234, 0.17899978160858154, 0.22626392543315887, 0.161007359623909, 0.2378622144460678, 0.13904744386672974, 0.19093330204486847, 0.16312561929225922, 0.1991412192583084, 0.21712833642959595, 0.20328524708747864, 0.15674877166748047, 0.1592620462179184, 0.20090849697589874, 0.2749909460544586, 0.3192765414714813, 0.26714298129081726, 0.2532467544078827, 0.206445574760437, 0.18817263841629028, 0.20611971616744995, 0.14669673144817352, 0.15370167791843414, 0.21404384076595306, 0.20061805844306946, 0.21172019839286804, 0.22421976923942566, 0.2306222915649414, 0.2149066925048828, 0.2403324991464615, 0.2865433692932129, 0.1747286170721054, 0.16238588094711304, 0.269313246011734, 0.19834807515144348, 0.21118614077568054, 0.24724633991718292, 0.20992305874824524, 0.14285501837730408, 0.2832360565662384, 0.1162256971001625, 0.24973170459270477, 0.3090580105781555, 0.16467513144016266, 0.2014167308807373, 0.20115382969379425, 0.15022464096546173, 0.2281769961118698, 0.21297407150268555, 0.22805841267108917, 0.2359616756439209, 0.19946563243865967, 0.2478501796722412, 0.23158179223537445, 0.239608496427536, 0.22348326444625854, 0.20930664241313934, 0.18881793320178986, 0.23569826781749725, 0.1870628446340561, 0.17053665220737457, 0.24981792271137238, 0.21019193530082703, 0.1995205134153366, 0.2945632338523865, 0.2526591122150421, 0.19384410977363586, 0.15783405303955078, 0.24385173618793488, 0.23009321093559265, 0.19119296967983246, 0.21875517070293427, 0.2675558924674988, 0.20025187730789185, 0.17440839111804962, 0.14238771796226501, 0.2587328553199768, 0.16477850079536438, 0.20183059573173523, 0.14503870904445648, 0.18931174278259277, 0.2319066971540451, 0.22707435488700867, 0.19118642807006836, 0.19517302513122559, 0.2400057166814804, 0.17711175978183746, 0.22010180354118347, 0.22304922342300415, 0.21565788984298706, 0.21581697463989258, 0.316050261259079, 0.17362044751644135, 0.22958336770534515, 0.19470511376857758, 0.2152358591556549, 0.21722234785556793, 0.2684018015861511, 0.15686121582984924, 0.1864154040813446, 0.21361559629440308, 0.24022997915744781, 0.26818034052848816, 0.13848243653774261, 0.2374688684940338, 0.2339789867401123, 0.13609622418880463, 0.1982341855764389, 0.24737514555454254, 0.2326786369085312, 0.2225615680217743, 0.1516052782535553, 0.23860988020896912, 0.34098154306411743, 0.15902023017406464, 0.28296777606010437, 0.2177528589963913, 0.17741230130195618, 0.27771174907684326, 0.2344971001148224, 0.22828756272792816, 0.18407787382602692, 0.17795857787132263, 0.14982372522354126, 0.2557084262371063, 0.17559123039245605, 0.1826971024274826, 0.2527763247489929, 0.19035454094409943, 0.1625966727733612, 0.16703736782073975, 0.2511385977268219, 0.18474982678890228, 0.2165530025959015, 0.17323391139507294, 0.2068864405155182, 0.17244188487529755, 0.2537406086921692, 0.223683163523674, 0.24290412664413452, 0.24726755917072296, 0.19823752343654633, 0.22679546475410461, 0.13327278196811676, 0.22899261116981506, 0.25739017128944397, 0.16607920825481415, 0.2941354811191559, 0.19562655687332153, 0.2587517499923706, 0.2179103046655655, 0.2347525805234909, 0.15747401118278503, 0.12899746000766754, 0.19030345976352692, 0.22319650650024414, 0.23039254546165466, 0.22129195928573608, 0.2459527850151062, 0.24318444728851318, 0.22439604997634888, 0.24569368362426758, 0.2081720530986786, 0.24561576545238495, 0.16471953690052032, 0.23444198071956635, 0.20924514532089233, 0.31392207741737366, 0.21015913784503937, 0.224387988448143, 0.20280294120311737, 0.2557244598865509, 0.24435970187187195, 0.23388993740081787, 0.2063496708869934, 0.195126011967659, 0.278321236371994, 0.20049941539764404, 0.25180113315582275, 0.21072986721992493, 0.20822153985500336, 0.2820880115032196, 0.2083660215139389, 0.2579600512981415, 0.22762469947338104, 0.20658248662948608, 0.21535301208496094, 0.21220524609088898, 0.1872629076242447, 0.23783542215824127, 0.23773567378520966, 0.23521216213703156, 0.21172159910202026, 0.2090318500995636, 0.20348913967609406, 0.20002245903015137, 0.23112548887729645, 0.2533005475997925, 0.2578904628753662, 0.23441942036151886, 0.2697846591472626, 0.27143406867980957, 0.22095176577568054, 0.19746875762939453, 0.2282112091779709, 0.2740015387535095, 0.1896071434020996, 0.23487387597560883, 0.2393859177827835, 0.22249354422092438, 0.3281380534172058, 0.2205694317817688, 0.22124210000038147, 0.21574464440345764, 0.17045123875141144, 0.20429225265979767, 0.20826363563537598, 0.2137387990951538, 0.22556696832180023, 0.1655968576669693, 0.276557058095932, 0.2741764187812805, 0.229605033993721, 0.1721585988998413, 0.27120429277420044, 0.21149319410324097, 0.1898714005947113, 0.19170032441616058, 0.2649777829647064, 0.21963366866111755, 0.16240011155605316, 0.27353158593177795, 0.2115851193666458, 0.1495143324136734, 0.1536020040512085, 0.22595447301864624, 0.21516017615795135, 0.17316024005413055, 0.21400761604309082, 0.20512889325618744, 0.21365435421466827, 0.18896876275539398, 0.28120407462120056, 0.17762111127376556, 0.20797669887542725, 0.24180173873901367, 0.20708227157592773, 0.17276088893413544, 0.23231101036071777, 0.20367658138275146, 0.19081446528434753, 0.27380242943763733, 0.24240680038928986, 1.4818466901779175, 3.221550941467285, 2.644575834274292, 1.3084337711334229, 1.3480443954467773, 1.9419403076171875, 1.6117072105407715, 2.63720703125, 2.652064085006714, 2.707268238067627, 3.056138753890991, 1.5991274118423462, 1.7835344076156616, 2.0524606704711914, 3.4867992401123047, 1.783120036125183, 2.0641682147979736, 2.4987692832946777, 2.4888997077941895, 2.0477049350738525, 1.978924036026001, 1.8430111408233643, 2.756706714630127, 1.4927057027816772, 1.9952213764190674, 1.751674771308899, 1.6613733768463135, 2.1681125164031982, 2.9410152435302734, 1.3915557861328125, 2.9151251316070557, 2.398221015930176, 2.3007748126983643, 1.7692303657531738, 2.111984968185425, 1.3467973470687866, 2.596729040145874, 2.844151020050049, 1.9368711709976196, 2.1245667934417725, 2.834275484085083, 2.08575439453125, 2.7442097663879395, 2.749620199203491, 2.7145614624023438, 1.9125301837921143, 1.9909250736236572, 3.125032901763916, 2.496119976043701, 1.4413002729415894, 1.6897954940795898, 2.4135351181030273, 2.0605223178863525, 2.299422025680542, 1.606325626373291, 2.369027614593506, 2.33075213432312, 1.6825300455093384, 1.3685413599014282, 2.0608067512512207, 2.0617082118988037, 1.7562683820724487, 1.5949746370315552, 1.7685680389404297, 2.514718770980835, 3.012638568878174, 1.867881178855896, 1.5605688095092773, 1.536818504333496, 3.257338285446167, 3.0255672931671143, 1.2612977027893066, 2.661566734313965, 1.5257482528686523, 2.9814083576202393, 2.577002763748169, 1.9539823532104492, 1.420182466506958, 3.1868507862091064, 2.024263620376587, 2.5870232582092285, 2.1841046810150146, 2.1172077655792236, 1.760011911392212, 1.5392347574234009, 1.8642419576644897, 2.1177682876586914, 2.262820243835449, 2.397352457046509, 2.662736177444458, 2.0595414638519287, 2.1762747764587402, 2.1965179443359375, 1.522676944732666, 1.3464547395706177, 2.8706557750701904, 2.3114285469055176, 1.9475622177124023, 1.7701377868652344, 1.9214937686920166, 1.6182432174682617, 2.2484750747680664, 2.45501708984375, 1.4179598093032837, 2.797977924346924, 2.3061773777008057, 2.2461774349212646, 2.573133707046509, 1.960191011428833, 2.100128173828125, 2.1534972190856934, 1.9618661403656006, 3.5673129558563232, 1.789628267288208, 2.165794849395752, 2.5966877937316895, 3.1496849060058594, 1.5759408473968506, 1.9234157800674438, 2.9242424964904785, 3.1507556438446045, 1.5079113245010376, 1.92497980594635, 3.1346328258514404, 1.7900632619857788, 2.2404069900512695, 2.2279679775238037, 2.1335878372192383, 2.9598019123077393, 2.8616578578948975, 2.550675630569458, 2.9524941444396973, 1.286926507949829, 2.181567668914795, 2.6226043701171875, 2.511167049407959, 2.1557607650756836, 2.918064594268799, 2.164975643157959, 1.6346909999847412, 2.363426685333252, 3.4181394577026367, 2.1539573669433594, 2.903987169265747, 1.7585328817367554, 1.8364171981811523, 2.660935640335083, 3.316087007522583, 3.1436095237731934, 2.0294041633605957, 1.4772804975509644, 2.23392915725708, 1.8567442893981934, 1.387594223022461, 2.379307746887207, 1.8263276815414429, 2.242001533508301, 1.7348296642303467, 1.4940677881240845, 2.9701664447784424, 2.011106252670288, 1.1992887258529663, 1.7724037170410156, 1.8615646362304688, 2.23844575881958, 2.653859853744507, 2.4800302982330322, 1.4806950092315674, 2.3738393783569336, 2.1662697792053223, 2.309811592102051, 1.4943417310714722, 2.949110746383667, 1.6933332681655884, 3.004425048828125, 2.1740427017211914, 2.1144700050354004, 1.5669549703598022, 1.2671306133270264, 2.8351070880889893, 1.934614658355713, 1.6059728860855103, 1.733390212059021, 2.324491024017334, 2.1090283393859863, 2.747884750366211, 3.1757524013519287, 1.5350173711776733, 2.0558090209960938, 3.022857666015625, 2.7589995861053467, 1.8036409616470337, 1.4971634149551392, 2.0819990634918213, 1.8116645812988281, 1.518496036529541, 2.068619728088379, 1.665755271911621, 3.306318998336792, 1.3811085224151611, 1.7760632038116455, 2.460641622543335, 2.647681474685669, 2.612760543823242, 1.9660459756851196, 1.436004638671875, 2.093494176864624, 2.0000810623168945, 1.6860747337341309, 2.954274892807007, 2.2310712337493896, 1.8303747177124023, 1.6369414329528809, 2.371349334716797, 1.9079140424728394, 3.1244022846221924, 2.0846471786499023, 1.8690176010131836, 1.5472856760025024, 1.8167492151260376, 2.718449115753174, 1.5804628133773804, 1.879690170288086, 3.3403987884521484, 2.3842406272888184, 1.8541420698165894, 1.7196346521377563, 1.6574982404708862, 1.9359318017959595, 2.7840428352355957, 1.417744517326355, 1.893739938735962, 1.8965837955474854, 1.751672625541687, 2.0153021812438965, 1.9364027976989746, 1.970231533050537, 1.644015908241272, 1.552419662475586, 1.4824243783950806, 1.6842867136001587, 2.3975791931152344, 2.002469539642334, 2.1970014572143555, 1.982503890991211, 3.1639013290405273, 1.9514715671539307, 1.8351366519927979, 2.122039794921875, 2.997657060623169, 2.318298101425171, 1.8031190633773804, 1.7508465051651, 3.083483934402466, 1.765321969985962, 2.180468797683716, 2.032413959503174, 2.539870023727417, 2.909679412841797, 2.9642763137817383, 2.584118604660034, 2.038444995880127, 1.4871124029159546, 1.565613031387329, 1.5673531293869019, 1.840651512145996, 2.7402563095092773, 2.0458486080169678, 3.241162061691284, 2.087745428085327, 2.5179965496063232, 2.387197732925415, 2.3133180141448975, 2.832796573638916, 2.2438735961914062, 1.5303068161010742, 2.632542133331299, 2.6927075386047363, 1.7257177829742432, 1.5173126459121704, 2.943267822265625, 2.3594090938568115, 1.692193865776062, 1.4942299127578735, 2.671903133392334, 2.227342367172241, 2.235050678253174, 2.143548011779785, 2.2828257083892822, 2.125500202178955, 2.5026135444641113, 2.864872932434082, 2.3733713626861572, 2.5690436363220215, 2.110691547393799, 1.4620952606201172, 2.6211299896240234, 2.92706298828125, 1.319350242614746, 2.5668225288391113, 225.1902313232422, 189.26280212402344, 127.0009994506836, 287.95281982421875, 158.9470672607422, 292.2208251953125, 84.3153076171875, 150.7158966064453, 266.0384521484375, 80.26752471923828, 404.7071838378906, 43.33168411254883, 48.8341064453125, 161.97193908691406, 274.5947265625, 145.14508056640625, 196.05133056640625, 58.50393295288086, 185.58624267578125, 83.28341674804688, 210.64126586914062, 62.247352600097656, 83.79805755615234, 237.03094482421875, 215.01333618164062, 90.02565002441406, 230.41954040527344, 306.2056884765625, 116.87507629394531, 130.96292114257812, 61.61520004272461, 57.18942642211914, 109.071044921875, 155.01339721679688, 212.08767700195312, 100.12813568115234, 97.86495971679688, 40.1751708984375, 368.9647521972656, 35.28936767578125, 103.94951629638672, 96.46701049804688, 178.53941345214844, 83.26378631591797, 211.2376251220703, 117.32036590576172, 232.3056640625, 111.5544204711914, 224.34600830078125, 82.69629669189453, 344.4710998535156, 211.63792419433594, 211.1156463623047, 60.88272476196289, 215.5546875, 337.4783630371094, 121.72814178466797, 45.46435546875, 177.8372344970703, 169.6484375, 82.65081787109375, 254.06668090820312, 243.18997192382812, 409.9195251464844, 91.13543701171875, 180.2989044189453, 118.93926239013672, 68.5433349609375, 95.8206787109375, 57.01934814453125, 220.950439453125, 137.06996154785156, 114.44493865966797, 80.48904418945312, 56.918212890625, 162.64846801757812, 116.89927673339844, 109.07086944580078, 55.76776123046875, 433.1328125, 128.51129150390625, 488.3133544921875, 53.827880859375, 142.4876708984375, 89.927978515625, 99.78681182861328, 145.8909149169922, 179.5364990234375, 247.86448669433594, 234.8617706298828, 65.71172332763672, 363.9403076171875, 108.80870819091797, 178.7862091064453, 262.9921875, 196.4499053955078, 37.4580192565918, 63.905975341796875, 35.64697265625, 107.3907470703125, 355.78961181640625, 195.1552276611328, 164.78858947753906, 130.44769287109375, 142.39662170410156, 73.123291015625, 132.96218872070312, 48.57144546508789, 64.751953125, 127.97637176513672, 132.83099365234375, 145.27398681640625, 183.6169891357422, 108.25255584716797, 94.12163543701172, 170.6972198486328, 347.0968017578125, 244.2900390625, 217.487060546875, 479.66046142578125, 107.95952606201172, 185.0179443359375, 243.8081817626953, 169.3944549560547, 93.968017578125, 148.83245849609375, 105.45035552978516, 142.00057983398438, 83.7269287109375, 81.1657485961914, 83.80716705322266, 250.7685546875, 172.29339599609375, 203.62217712402344, 344.9562072753906, 62.758514404296875, 102.53199005126953, 40.51848602294922, 234.49288940429688, 87.36294555664062, 107.19644927978516, 251.0507354736328, 73.304443359375, 72.9844970703125, 143.63348388671875, 115.1834716796875, 137.54046630859375, 213.0623779296875, 185.423583984375, 100.61388397216797, 398.9533386230469, 56.33498001098633, 219.6571807861328, 90.36222076416016, 35.95986557006836, 104.31263732910156, 150.54454040527344, 224.6015625, 48.4915771484375, 190.8360137939453, 269.7655029296875, 136.79180908203125, 99.35665130615234, 105.0799560546875, 226.7871856689453, 146.8546600341797, 243.00067138671875, 70.65475463867188, 224.1739044189453, 72.0980224609375, 152.0155029296875, 113.46671295166016, 267.8448791503906, 196.1034698486328, 196.487060546875, 40.43629455566406, 201.46826171875, 194.81761169433594, 190.4326934814453, 127.583251953125, 181.2951202392578, 185.123779296875, 261.98016357421875, 68.7555160522461, 178.7412872314453, 133.65362548828125, 410.32373046875, 66.2882080078125, 253.69456481933594, 152.26910400390625, 171.14874267578125, 242.9763946533203, 126.01383209228516, 80.89083099365234, 85.43946838378906, 88.3740234375, 172.8291015625, 299.27947998046875, 278.7763671875, 326.47174072265625, 157.64659118652344, 116.43708801269531, 205.92446899414062, 170.2126922607422, 310.90869140625, 224.27159118652344, 118.29595184326172, 214.88026428222656, 395.531005859375, 98.83295440673828, 116.93981170654297, 35.21820068359375, 45.8519287109375, 38.07391357421875, 79.68743896484375, 229.1893310546875, 202.86366271972656, 247.8837890625, 169.67100524902344, 78.59770965576172, 93.66207122802734, 344.0754699707031, 176.13409423828125, 55.9166259765625, 124.53157806396484, 82.68682098388672, 78.02066040039062, 151.5128936767578, 207.0857391357422, 140.07638549804688, 95.01374816894531, 308.7708435058594, 32.285072326660156, 101.62445068359375, 85.0425796508789, 220.65000915527344, 169.231201171875, 309.65875244140625, 226.3851318359375, 370.936279296875, 324.966796875, 80.35122680664062, 246.6975860595703, 119.56425476074219, 226.05419921875, 72.94828796386719, 409.6852111816406, 52.60125732421875, 171.9453125, 211.0682373046875, 157.07839965820312, 118.48236083984375, 365.38775634765625, 70.81561279296875, 254.650146484375, 192.4661865234375, 56.115047454833984, 144.17919921875, 106.84770965576172, 460.0416564941406, 92.2466812133789, 148.4856719970703, 147.63946533203125, 149.84249877929688, 111.09100341796875, 49.18939208984375, 79.92604064941406, 167.17068481445312, 287.8590087890625, 363.6507873535156, 374.5672912597656, 308.91729736328125, 207.26089477539062, 162.7294158935547, 117.9736099243164, 229.4491729736328, 264.3058776855469, 172.60948181152344, 236.9761199951172, 115.49614715576172, 32.70904541015625, 174.49832153320312, 146.25119018554688, 348.1183166503906, 40.264373779296875, 40.46234130859375, 211.60675048828125, 71.14398956298828, 45.93310546875, 235.0424041748047, 39.45459747314453, 107.892578125, 247.44204711914062, 74.49676513671875, 141.94651794433594, 132.41751098632812, 266.7976989746094, 68.7725830078125, 140.731689453125, 62.28314208984375, 2.7989838123321533, 3.0533690452575684, 1.8457683324813843, 1.996224284172058, 2.5183305740356445, 2.5780017375946045, 2.68217396736145, 4.024162292480469, 2.9122068881988525, 1.892991542816162, 1.5902622938156128, 3.25419545173645, 2.8156216144561768, 3.096686601638794, 2.8889782428741455, 1.326496958732605, 3.1391665935516357, 1.746328592300415, 3.1976513862609863, 2.072573661804199, 2.17305850982666, 3.5880229473114014, 2.9589128494262695, 2.3932015895843506, 2.7903740406036377, 2.044966697692871, 2.0088717937469482, 2.7639148235321045, 2.3558671474456787, 2.9157631397247314, 1.6644946336746216, 2.653794288635254, 3.4881200790405273, 1.526534080505371, 2.857297897338867, 2.9903512001037598, 3.5529279708862305, 2.214858055114746, 3.419417142868042, 2.703312873840332, 2.6877987384796143, 2.0164523124694824, 3.3152036666870117, 2.7889370918273926, 2.1334924697875977, 2.2440314292907715, 2.505801200866699, 2.2128496170043945, 3.48699688911438, 2.0664634704589844, 2.565730571746826, 2.881164073944092, 2.86559796333313, 1.8265389204025269, 2.2971785068511963, 2.2866907119750977, 3.1478967666625977, 1.9439454078674316, 2.2798874378204346, 2.9900505542755127, 3.4884023666381836, 2.856421947479248, 2.278946876525879, 2.2342872619628906, 2.531308650970459, 1.657452940940857, 1.2861300706863403, 3.213942289352417, 1.945931315422058, 3.367579936981201, 2.89144229888916, 1.8906792402267456, 3.1865074634552, 3.0743932723999023, 2.825944185256958, 2.781907796859741, 2.079899787902832, 2.4098291397094727, 2.2455930709838867, 2.136876106262207, 2.5464165210723877, 3.4453539848327637, 2.4026405811309814, 2.2983028888702393, 2.5534110069274902, 3.0430119037628174, 2.7319209575653076, 2.3866679668426514, 3.7269716262817383, 2.988206624984741, 1.5888930559158325, 3.805528163909912, 3.499751567840576, 2.9355874061584473, 1.7198882102966309, 1.8925145864486694, 3.9392788410186768, 2.412055015563965, 2.4620485305786133, 3.6937925815582275, 1.6910027265548706, 1.7335351705551147, 3.1392130851745605, 1.6660337448120117, 3.2011852264404297, 2.188857078552246, 3.564427375793457, 2.2988247871398926, 2.291351318359375, 2.616530418395996, 2.072432518005371, 2.659980297088623, 3.44616436958313, 2.5468950271606445, 2.530616283416748, 2.6290674209594727, 2.571328639984131, 2.570721387863159, 2.4773783683776855, 2.696148633956909, 2.423203945159912, 1.980521321296692, 2.9469714164733887, 3.429751396179199, 2.374781370162964, 1.539254069328308, 1.5756750106811523, 3.145848274230957, 3.5626537799835205, 2.9888031482696533, 3.0898046493530273, 2.245777130126953, 1.778767466545105, 3.3793694972991943, 2.180145502090454, 2.114992380142212, 3.423227071762085, 1.3750449419021606, 3.114269971847534, 2.081395149230957, 2.0641844272613525, 2.43949818611145, 3.199580669403076, 2.506985664367676, 1.365503191947937, 2.8740432262420654, 1.5141406059265137, 2.696181535720825, 2.004055976867676, 1.7351752519607544, 2.985478162765503, 3.4883294105529785, 3.348646879196167, 2.5530500411987305, 2.9595799446105957, 1.5586563348770142, 2.2823972702026367, 2.496272087097168, 2.510972023010254, 2.2713143825531006, 1.829982876777649, 3.2438290119171143, 2.688657522201538, 2.438807249069214, 3.4394524097442627, 3.113276720046997, 2.5947046279907227, 2.345078468322754, 2.958219289779663, 2.570223331451416, 2.828644275665283, 1.9938486814498901, 2.8891191482543945, 2.883988618850708, 3.2870476245880127, 3.383016347885132, 3.5201966762542725, 3.316838502883911, 2.9058337211608887, 2.1411261558532715, 3.206167459487915, 1.5061285495758057, 1.9108692407608032, 2.1095476150512695, 2.0130114555358887, 2.8088085651397705, 3.9429714679718018, 2.5796408653259277, 2.4626169204711914, 1.9803322553634644, 1.9204164743423462, 2.111884355545044, 2.664517879486084, 3.1810503005981445, 3.9906089305877686, 4.028165817260742, 2.11415958404541, 2.4516918659210205, 1.79350745677948, 1.4941948652267456, 2.9525203704833984, 3.228083610534668, 1.6904610395431519, 3.186598539352417, 2.368190288543701, 3.3933093547821045, 3.3130176067352295, 1.8003628253936768, 3.1814513206481934, 1.978352665901184, 2.8383007049560547, 1.6101326942443848, 1.5689748525619507, 2.3205957412719727, 2.478276252746582, 2.995257616043091, 2.073509454727173, 2.5567426681518555, 3.274034023284912, 2.9140591621398926, 1.8470467329025269, 3.0850207805633545, 2.007154703140259, 2.2380142211914062, 2.9302279949188232, 2.754870653152466, 3.310246229171753, 3.123669147491455, 3.410313606262207, 2.61307430267334, 2.69960880279541, 3.3758819103240967, 3.0294432640075684, 2.6075756549835205, 2.6679887771606445, 2.7691779136657715, 2.831505060195923, 3.74993634223938, 3.082895517349243, 3.7180540561676025, 3.156292676925659, 2.703294038772583, 2.3381338119506836, 3.2224645614624023, 2.076291084289551, 3.703341484069824, 2.140854835510254, 2.5603604316711426, 1.6002819538116455, 3.757571220397949, 2.738981246948242, 1.6455849409103394, 2.7120354175567627, 3.0525543689727783, 3.202733039855957, 3.5008654594421387, 3.5277035236358643, 2.18859601020813, 2.8149895668029785, 3.111199378967285, 2.7824699878692627, 2.5245726108551025, 1.6814641952514648, 1.4353437423706055, 2.780705451965332, 2.1774373054504395, 1.1402486562728882, 2.5228030681610107, 2.7269933223724365, 3.9325151443481445, 2.1268043518066406, 1.5049755573272705, 1.754231333732605, 2.0133681297302246, 2.9881591796875, 1.458626627922058, 3.646378755569458, 2.274014949798584, 2.0106096267700195, 1.6026690006256104, 2.305286407470703, 1.9187246561050415, 2.3964624404907227, 2.894528388977051, 2.51788330078125, 2.6368188858032227, 3.0490922927856445, 3.6779050827026367, 1.7991819381713867, 3.142252206802368, 3.076582908630371, 2.0378963947296143, 3.3977420330047607, 2.3435914516448975, 2.2324094772338867, 2.8979110717773438, 2.2042245864868164, 2.0238986015319824, 2.3494670391082764, 3.029162645339966, 0.2145504653453827, 0.1779223531484604, 0.23746457695960999, 0.2911010682582855, 0.21755915880203247, 0.29154983162879944, 0.2092190533876419, 0.228080153465271, 0.23939824104309082, 0.17430374026298523, 0.23738501965999603, 0.18164896965026855, 0.18962441384792328, 0.23727908730506897, 0.20837214589118958, 0.20926928520202637, 0.27317291498184204, 0.17024348676204681, 0.3030383586883545, 0.18135535717010498, 0.20089396834373474, 0.2300669252872467, 0.2708947956562042, 0.2068694680929184, 0.20937782526016235, 0.20159144699573517, 0.18467018008232117, 0.2241654396057129, 0.1782616823911667, 0.28449392318725586, 0.21533767879009247, 0.2171449065208435, 0.22174303233623505, 0.2029864490032196, 0.2242175191640854, 0.19471509754657745, 0.2200106829404831, 0.2670987546443939, 0.19867610931396484, 0.28070247173309326, 0.21161314845085144, 0.1910579949617386, 0.2400805652141571, 0.2086421102285385, 0.19052593410015106, 0.16037726402282715, 0.19664409756660461, 0.2148822396993637, 0.19320423901081085, 0.2109159231185913, 0.16786380112171173, 0.22131595015525818, 0.15194156765937805, 0.23961670696735382, 0.20834438502788544, 0.15269684791564941, 0.16660399734973907, 0.17814941704273224, 0.17130732536315918, 0.19221347570419312, 0.23788678646087646, 0.19228315353393555, 0.2512965798377991, 0.209813192486763, 0.27512121200561523, 0.17527270317077637, 0.2150266170501709, 0.25406160950660706, 0.22127144038677216, 0.18842971324920654, 0.25282856822013855, 0.2196236401796341, 0.17774134874343872, 0.20106853544712067, 0.21572920680046082, 0.24354110658168793, 0.18564975261688232, 0.16834647953510284, 0.14507167041301727, 0.23420146107673645, 0.25009584426879883, 0.21970580518245697, 0.22009027004241943, 0.23652003705501556, 0.21000368893146515, 0.2341109812259674, 0.15733611583709717, 0.2502165138721466, 0.21377918124198914, 0.2234758734703064, 0.23524920642375946, 0.18334417045116425, 0.23839446902275085, 0.19427619874477386, 0.30864280462265015, 0.19188685715198517, 0.24265168607234955, 0.15728184580802917, 0.22980263829231262, 0.17124924063682556, 0.16435061395168304, 0.2349318116903305, 0.2820482850074768, 0.24101980030536652, 0.23748371005058289, 0.21623872220516205, 0.1881701648235321, 0.21454036235809326, 0.21359725296497345, 0.2772631049156189, 0.1605546474456787, 0.1463104486465454, 0.32167860865592957, 0.21591006219387054, 0.23151077330112457, 0.1665431410074234, 0.32246869802474976, 0.25349104404449463, 0.2366432547569275, 0.25801411271095276, 0.2324242889881134, 0.19780917465686798, 0.23299327492713928, 0.20657317340373993, 0.19666419923305511, 0.2369859218597412, 0.22217798233032227, 0.18461166322231293, 0.21150065958499908, 0.23176467418670654, 0.2565769851207733, 0.2625589966773987, 0.2155633121728897, 0.155130535364151, 0.19733436405658722, 0.24562866985797882, 0.22392170131206512, 0.2242303043603897, 0.21027334034442902, 0.2595071494579315, 0.16007477045059204, 0.1993548572063446, 0.14438585937023163, 0.22098670899868011, 0.21216613054275513, 0.19783499836921692, 0.25513511896133423, 0.2038465142250061, 0.1516404002904892, 0.1967051476240158, 0.2650515139102936, 0.18125803768634796, 0.18339323997497559, 0.17917285859584808, 0.26575326919555664, 0.2232169657945633, 0.18134057521820068, 0.2674641013145447, 0.23370906710624695, 0.18205778300762177, 0.1973605751991272, 0.18507884442806244, 0.2145175188779831, 0.2539474666118622, 0.1790759265422821, 0.23231196403503418, 0.27354374527931213, 0.19497504830360413, 0.18914631009101868, 0.18081848323345184, 0.2390243411064148, 0.19413836300373077, 0.21083563566207886, 0.18235091865062714, 0.19155162572860718, 0.2149214893579483, 0.24352073669433594, 0.12104342132806778, 0.2401229590177536, 0.19113489985466003, 0.24384631216526031, 0.23500090837478638, 0.2632940709590912, 0.16196933388710022, 0.2655453383922577, 0.25183117389678955, 0.20757730305194855, 0.21518626809120178, 0.23267647624015808, 0.18428008258342743, 0.2690700888633728, 0.12494954466819763, 0.20553182065486908, 0.21890616416931152, 0.14369231462478638, 0.21007251739501953, 0.1950155794620514, 0.17094145715236664, 0.19653110206127167, 0.22522155940532684, 0.18576329946517944, 0.19767719507217407, 0.23599852621555328, 0.19717025756835938, 0.22759196162223816, 0.22411730885505676, 0.21481956541538239, 0.17729489505290985, 0.2688329517841339, 0.179069384932518, 0.16562767326831818, 0.19140975177288055, 0.1494220495223999, 0.22808034718036652, 0.2464274913072586, 0.23240184783935547, 0.18803484737873077, 0.25713908672332764, 0.2202180027961731, 0.24541686475276947, 0.2201293259859085, 0.16304703056812286, 0.17677146196365356, 0.21659055352210999, 0.17553049325942993, 0.2000214010477066, 0.21797631680965424, 0.26001468300819397, 0.16167941689491272, 0.22738440334796906, 0.1714175045490265, 0.19843819737434387, 0.17128203809261322, 0.1455196738243103, 0.2138780951499939, 0.2219192385673523, 0.15729357302188873, 0.21158470213413239, 0.22334985435009003, 0.2622678577899933, 0.2226489931344986, 0.23581092059612274, 0.1508173942565918, 0.16702723503112793, 0.2061154842376709, 0.19055263698101044, 0.24911421537399292, 0.2074802666902542, 0.24550983309745789, 0.18364794552326202, 0.22261971235275269, 0.1609976887702942, 0.26810741424560547, 0.2077832818031311, 0.11333633214235306, 0.25942179560661316, 0.2598080039024353, 0.2139906883239746, 0.2123475968837738, 0.23600894212722778, 0.22767947614192963, 0.2512848675251007, 0.2084382027387619, 0.20678070187568665, 0.33140116930007935, 0.23022116720676422, 0.25692984461784363, 0.14196288585662842, 0.21099203824996948, 0.2374120056629181, 0.20047715306282043, 0.2097361832857132, 0.3187580108642578, 0.1712835282087326, 0.25981226563453674, 0.2215716689825058, 0.26990750432014465, 0.21340201795101166, 0.2168470323085785, 0.21544429659843445, 0.25021716952323914, 0.2153419852256775, 0.146542027592659, 0.153153657913208, 0.2567744255065918, 0.22019203007221222, 0.19976139068603516, 0.2897670269012451, 0.2123650759458542, 0.16372203826904297, 0.30658048391342163, 0.19138602912425995, 0.19975152611732483, 0.22500872611999512, 0.18754638731479645, 0.20938535034656525, 0.268857479095459, 0.18308277428150177, 0.24516277015209198, 0.1660860776901245, 2.0888357162475586, 1.4378530979156494, 2.207841634750366, 1.6317335367202759, 2.2044425010681152, 2.568182945251465, 3.049980640411377, 2.258678436279297, 1.7750930786132812, 1.6634790897369385, 2.5924007892608643, 1.5925838947296143, 2.7329230308532715, 1.3790711164474487, 1.7119228839874268, 1.6107561588287354, 2.279083251953125, 1.843910813331604, 1.3708858489990234, 2.0534651279449463, 2.4298043251037598, 3.081022262573242, 2.427603244781494, 2.016462564468384, 1.6651586294174194, 3.225376844406128, 2.278832197189331, 1.268665075302124, 2.611574649810791, 2.46517276763916, 2.870342969894409, 1.4860596656799316, 2.8927853107452393, 1.7124676704406738, 2.7620468139648438, 1.6479735374450684, 1.6640625, 2.0727574825286865, 1.6882375478744507, 2.8057329654693604, 2.3160030841827393, 2.3027188777923584, 2.1489856243133545, 2.7854630947113037, 2.3545079231262207, 2.8270504474639893, 2.1279585361480713, 3.4204442501068115, 3.1886837482452393, 2.5400824546813965, 2.7685699462890625, 3.7184977531433105, 1.3832811117172241, 2.483538866043091, 2.696312427520752, 1.5342037677764893, 1.4716076850891113, 2.6191649436950684, 2.416177272796631, 1.5110031366348267, 2.2494375705718994, 2.439089059829712, 2.611776113510132, 3.0076656341552734, 2.858140230178833, 2.119786262512207, 2.302830219268799, 2.3363966941833496, 1.8956648111343384, 2.2251434326171875, 2.026463031768799, 3.0874950885772705, 1.231223464012146, 3.3367414474487305, 2.6444149017333984, 1.5294218063354492, 1.6052078008651733, 1.5911186933517456, 1.2964346408843994, 1.5009104013442993, 1.5712881088256836, 1.5176118612289429, 3.2401530742645264, 1.8904482126235962, 3.105766773223877, 2.161546468734741, 2.0111682415008545, 1.7483690977096558, 2.6054604053497314, 2.50553297996521, 2.1980133056640625, 2.504209041595459, 1.6062074899673462, 2.2511534690856934, 1.3517440557479858, 2.0355277061462402, 2.141266345977783, 1.3453680276870728, 1.7245362997055054, 2.8164093494415283, 2.653897762298584, 2.39725923538208, 2.756831407546997, 2.9028661251068115, 2.322899341583252, 1.6905531883239746, 2.4745638370513916, 1.763468861579895, 1.8591461181640625, 2.7035651206970215, 3.1539812088012695, 2.8384315967559814, 2.037931442260742, 2.1102371215820312, 3.4614109992980957, 2.0059971809387207, 2.0026133060455322, 1.611834168434143, 1.907975435256958, 2.1408438682556152, 1.8515900373458862, 1.7137094736099243, 1.762856125831604, 2.3983335494995117, 1.769101619720459, 1.874275803565979, 2.2308998107910156, 1.5686695575714111, 2.59541654586792, 2.4688429832458496, 2.0370702743530273, 2.9250237941741943, 1.8110578060150146, 2.801957845687866, 3.1143157482147217, 1.915999412536621, 1.798392653465271, 1.7528181076049805, 1.790616512298584, 1.9088636636734009, 3.841491937637329, 2.443612813949585, 3.11840558052063, 2.4523425102233887, 2.5281617641448975, 2.2048988342285156, 1.6784882545471191, 2.122410774230957, 1.9500484466552734, 2.1264877319335938, 1.7127717733383179, 2.08583927154541, 1.66006338596344, 1.7457952499389648, 1.94017493724823, 2.4160165786743164, 1.7164369821548462, 2.033766746520996, 2.684443950653076, 2.338395833969116, 1.9193458557128906, 1.5587583780288696, 2.4474024772644043, 2.2658333778381348, 2.329457998275757, 2.746314287185669, 2.23507022857666, 3.1924633979797363, 1.9131677150726318, 2.9865245819091797, 2.018012285232544, 2.632798433303833, 3.246068000793457, 3.0545644760131836, 2.137993812561035, 2.235135078430176, 2.5702617168426514, 2.3426754474639893, 1.5613994598388672, 2.0375759601593018, 2.147709369659424, 2.573676586151123, 2.722043991088867, 2.253375768661499, 3.893946409225464, 2.7102997303009033, 3.3901970386505127, 3.99192214012146, 2.413973569869995, 2.387183904647827, 3.145953893661499, 2.9016149044036865, 2.156843423843384, 1.6993612051010132, 2.0631489753723145, 2.700342893600464, 1.786436676979065, 2.046065092086792, 1.5958890914916992, 4.037653923034668, 2.051600456237793, 2.047605514526367, 2.5955586433410645, 2.9155242443084717, 1.8785234689712524, 1.7348458766937256, 1.808549165725708, 1.8966583013534546, 1.8373262882232666, 2.42687726020813, 2.73915958404541, 1.7965208292007446, 1.6851856708526611, 1.843492031097412, 1.647072672843933, 2.080955982208252, 2.128218650817871, 3.074284553527832, 2.061836004257202, 2.367654323577881, 2.4291892051696777, 1.567234754562378, 2.0798428058624268, 1.8259626626968384, 3.478081226348877, 2.201914072036743, 2.5854711532592773, 2.5134129524230957, 2.6539933681488037, 2.349259614944458, 1.6229743957519531, 1.8647435903549194, 1.7445520162582397, 2.656259775161743, 1.8768818378448486, 2.381654977798462, 1.8390270471572876, 2.2188122272491455, 2.6351876258850098, 3.2192883491516113, 1.562461256980896, 2.8576927185058594, 1.8852943181991577, 3.41227126121521, 2.4730441570281982, 2.0613760948181152, 2.0708258152008057, 2.1775097846984863, 1.7616465091705322, 2.915003538131714, 2.1979990005493164, 1.937103271484375, 2.5236921310424805, 1.384606957435608, 1.7858450412750244, 2.321280002593994, 3.033557653427124, 2.381288766860962, 1.9227491617202759, 2.8024368286132812, 2.4368205070495605, 2.82153058052063, 2.066382884979248, 2.340838670730591, 3.0453431606292725, 1.5496896505355835, 2.315547227859497, 3.474426507949829, 1.6358627080917358, 2.464430093765259, 3.03999924659729, 2.026505470275879, 1.749001383781433, 2.2309587001800537, 2.0969924926757812, 2.0372493267059326, 2.3437962532043457, 1.8077635765075684, 1.3620083332061768, 2.4136641025543213, 2.4124948978424072, 2.9560558795928955, 2.5614013671875, 2.11667799949646, 2.104949951171875, 2.4144015312194824, 1.46241295337677, 1.0942401885986328, 2.0766377449035645, 2.762826442718506, 2.7160918712615967, 2.9411137104034424, 1.5085572004318237, 1.9150850772857666, 2.5044021606445312, 1.7299118041992188, 2.006117820739746, 1.8190215826034546, 2.09427809715271, 1.9084398746490479, 147.231201171875, 326.6433410644531, 306.5899658203125, 90.01651000976562, 311.3542785644531, 87.31024169921875, 265.9510498046875, 132.7371826171875, 345.8722229003906, 143.53623962402344, 349.3175354003906, 292.14007568359375, 237.64468383789062, 126.45857238769531, 182.2448272705078, 192.813232421875, 98.46844482421875, 304.050537109375, 328.69537353515625, 105.8724365234375, 167.68798828125, 127.42767333984375, 280.1474609375, 179.337646484375, 124.07611083984375, 257.7351379394531, 143.6885986328125, 28.90922737121582, 264.26678466796875, 229.84814453125, 164.750732421875, 93.07489013671875, 246.25164794921875, 59.81221389770508, 125.4876708984375, 289.3894958496094, 223.6734161376953, 256.3065185546875, 202.05252075195312, 146.16346740722656, 93.6494140625, 33.1453857421875, 101.2416000366211, 187.9263458251953, 46.48798751831055, 116.76165771484375, 351.72607421875, 275.3199462890625, 275.47113037109375, 179.7497100830078, 166.68028259277344, 51.1741943359375, 190.2428741455078, 187.1806182861328, 76.93750762939453, 265.60260009765625, 242.4583740234375, 108.89715576171875, 98.60607147216797, 306.6639709472656, 140.96585083007812, 206.1180877685547, 52.54901123046875, 304.09088134765625, 113.40785217285156, 55.58071517944336, 157.17623901367188, 325.015380859375, 183.68760681152344, 50.05893325805664, 249.8682403564453, 281.04071044921875, 257.3975524902344, 233.88641357421875, 207.9862060546875, 188.6737518310547, 98.4300537109375, 154.35748291015625, 206.77374267578125, 373.6551818847656, 384.8215026855469, 141.28402709960938, 150.66891479492188, 184.790771484375, 112.0682373046875, 79.36737823486328, 105.21636199951172, 38.75146484375, 132.43963623046875, 142.872314453125, 71.35481262207031, 73.2509765625, 157.4110107421875, 211.72073364257812, 165.64144897460938, 243.0301055908203, 220.08245849609375, 254.0574493408203, 233.0855255126953, 42.970027923583984, 82.93562316894531, 97.73320770263672, 180.2392578125, 115.20173645019531, 80.1523208618164, 148.6508331298828, 296.18798828125, 106.51531982421875, 220.68572998046875, 69.11844635009766, 61.29946517944336, 116.99544525146484, 307.4112548828125, 118.35499572753906, 200.8095703125, 32.6065673828125, 171.11557006835938, 122.78778076171875, 246.7060546875, 57.968505859375, 252.9942169189453, 50.95159912109375, 88.83721160888672, 220.650146484375, 133.25889587402344, 420.4845275878906, 42.70254135131836, 189.08518981933594, 341.0196838378906, 218.8721466064453, 340.12408447265625, 552.1756591796875, 152.88119506835938, 71.17153930664062, 329.33953857421875, 152.3603057861328, 151.33010864257812, 200.4632110595703, 84.74556732177734, 168.4784393310547, 438.25421142578125, 46.95355224609375, 38.30141830444336, 57.4996223449707, 213.69903564453125, 279.49761962890625, 217.24560546875, 45.4422607421875, 171.9267578125, 176.6854248046875, 146.51658630371094, 235.33230590820312, 319.42822265625, 163.88742065429688, 165.040771484375, 91.92147064208984, 36.87152099609375, 197.8828887939453, 231.9763946533203, 120.79828643798828, 122.936279296875, 601.1943359375, 219.74249267578125, 134.43655395507812, 156.91357421875, 242.32632446289062, 174.31411743164062, 213.23155212402344, 115.9281005859375, 60.45880889892578, 132.3527374267578, 159.63363647460938, 283.79205322265625, 66.46161651611328, 263.7061767578125, 203.63751220703125, 106.00433349609375, 77.23868560791016, 52.0281982421875, 252.7841796875, 75.87939453125, 205.22206115722656, 336.523193359375, 319.22528076171875, 83.08846282958984, 264.0804443359375, 127.47000885009766, 501.451904296875, 157.5172576904297, 46.00870132446289, 171.84915161132812, 137.12289428710938, 214.85818481445312, 331.2220153808594, 341.24383544921875, 485.6502990722656, 239.74560546875, 73.20148468017578, 216.1995849609375, 236.32101440429688, 180.54640197753906, 97.14862060546875, 224.30889892578125, 91.00809478759766, 104.68781280517578, 168.67233276367188, 124.36650848388672, 46.805477142333984, 50.20383834838867, 41.24575424194336, 113.83929443359375, 293.19573974609375, 69.8660888671875, 411.23779296875, 246.8515625, 225.37820434570312, 102.1815185546875, 231.77964782714844, 177.20785522460938, 37.56643295288086, 380.1531982421875, 277.4444885253906, 113.47535705566406, 148.8427734375, 160.03521728515625, 137.94467163085938, 104.723388671875, 199.78445434570312, 63.882568359375, 130.5106201171875, 86.52171325683594, 388.4067077636719, 153.01815795898438, 158.5980682373047, 132.71397399902344, 177.70921325683594, 134.47544860839844, 81.9305419921875, 207.06036376953125, 164.2509307861328, 341.74285888671875, 67.74222564697266, 325.70208740234375, 46.669677734375, 29.06475830078125, 212.44189453125, 215.51788330078125, 123.24321746826172, 70.8660888671875, 103.78564453125, 109.45464324951172, 83.06499481201172, 284.13201904296875, 54.634403228759766, 237.4735107421875, 183.676513671875, 87.9949722290039, 168.3434295654297, 182.9599609375, 60.816463470458984, 72.26647186279297, 314.875, 378.3563232421875, 280.35748291015625, 160.64581298828125, 210.6151580810547, 297.4442138671875, 85.7464599609375, 120.132568359375, 83.0450210571289, 170.1404266357422, 56.576416015625, 70.21143341064453, 251.8916015625, 82.74922943115234, 196.3470458984375, 300.9621276855469, 65.60899353027344, 45.121307373046875, 178.1229705810547, 112.7955322265625, 213.1296844482422, 308.458740234375, 135.96173095703125, 33.042091369628906, 226.282470703125, 289.5233154296875, 252.83045959472656, 168.1941375732422, 277.91217041015625, 325.32568359375, 215.23312377929688, 137.77114868164062, 124.88130950927734, 145.044677734375, 162.8269500732422, 248.9052734375, 44.15090560913086, 66.76764678955078, 93.2985610961914, 2.5519235134124756, 2.659985303878784, 2.113295555114746, 1.391090989112854, 1.7527703046798706, 2.2343645095825195, 1.779727578163147, 1.5205564498901367, 1.615920066833496, 2.056851387023926, 2.2781832218170166, 2.5574328899383545, 2.114445686340332, 3.4969053268432617, 1.8583343029022217, 2.932499408721924, 3.243809700012207, 3.46557354927063, 2.6560258865356445, 3.2577342987060547, 3.38033127784729, 3.0156338214874268, 1.22590172290802, 2.115802049636841, 2.9893524646759033, 3.307561159133911, 1.6269254684448242, 1.3767708539962769, 2.538510322570801, 1.4600982666015625, 1.770729899406433, 3.2741618156433105, 1.8631998300552368, 2.043255567550659, 3.0013058185577393, 3.1337292194366455, 2.472461700439453, 2.4452221393585205, 3.033646821975708, 2.574090003967285, 3.3558743000030518, 2.5468904972076416, 3.129216432571411, 1.84746253490448, 3.3870632648468018, 2.4318299293518066, 3.268543243408203, 2.2767515182495117, 4.192204475402832, 2.9982082843780518, 2.3226404190063477, 3.231945037841797, 2.293233633041382, 2.8910796642303467, 3.4176323413848877, 2.8994531631469727, 2.2096147537231445, 1.4936857223510742, 2.113621234893799, 3.436596632003784, 2.2590713500976562, 2.16616153717041, 3.199639320373535, 3.0747227668762207, 2.296078681945801, 2.116602897644043, 3.8955090045928955, 2.767925262451172, 2.3957033157348633, 2.35134220123291, 2.2646052837371826, 2.0961320400238037, 1.9465703964233398, 1.8232688903808594, 1.82036292552948, 3.247788429260254, 3.464592456817627, 1.9380346536636353, 3.170252561569214, 3.0185139179229736, 1.6555485725402832, 2.9008610248565674, 2.3062689304351807, 2.2188708782196045, 2.053851366043091, 3.188572883605957, 1.3957756757736206, 1.4960203170776367, 2.3100948333740234, 2.3636817932128906, 2.3141963481903076, 3.1070361137390137, 2.9119293689727783, 1.5293188095092773, 3.064335823059082, 3.4904091358184814, 2.8911778926849365, 2.9590368270874023, 2.6446197032928467, 3.65775203704834, 2.273911476135254, 1.54497230052948, 2.9782774448394775, 2.9285888671875, 1.5685491561889648, 2.034787178039551, 3.5005300045013428, 2.5678458213806152, 4.39034366607666, 1.803303837776184, 3.3495874404907227, 3.622836112976074, 2.6691315174102783, 2.1172947883605957, 1.7352476119995117, 2.209996223449707, 3.7618420124053955, 1.780732274055481, 2.202390193939209, 2.468165636062622, 2.883728504180908, 2.2510664463043213, 3.9084577560424805, 2.120312452316284, 2.927824020385742, 2.7154335975646973, 1.7890586853027344, 2.5722744464874268, 2.7162792682647705, 1.9289902448654175, 1.3319473266601562, 3.4417009353637695, 3.9100847244262695, 2.1961400508880615, 2.4219980239868164, 2.9545183181762695, 2.0567197799682617, 1.6063997745513916, 3.0561439990997314, 3.307101249694824, 1.808510661125183, 3.2930543422698975, 2.1819145679473877, 2.052151679992676, 3.0842504501342773, 2.433809757232666, 3.058547258377075, 1.4581680297851562, 2.658501625061035, 2.7109532356262207, 2.803415536880493, 2.922816514968872, 3.1333022117614746, 2.954061269760132, 2.725226402282715, 3.8762388229370117, 3.755044460296631, 3.3835668563842773, 1.8417633771896362, 1.6904640197753906, 2.776850461959839, 1.5388638973236084, 1.8359583616256714, 3.673407554626465, 2.928518056869507, 2.8992767333984375, 2.36964750289917, 1.743874430656433, 2.5258302688598633, 2.3491296768188477, 2.7720787525177, 3.190220355987549, 2.7499911785125732, 3.324327230453491, 2.932055711746216, 2.696622848510742, 3.170825481414795, 3.9603071212768555, 2.9901230335235596, 2.6276679039001465, 3.145413637161255, 1.801603078842163, 3.4802465438842773, 2.3842978477478027, 2.102490186691284, 3.2023096084594727, 3.2527034282684326, 2.555732250213623, 1.6509685516357422, 1.682202696800232, 2.2155332565307617, 2.795459032058716, 2.876460552215576, 3.342637300491333, 1.8701905012130737, 2.108079195022583, 2.294806718826294, 2.2397775650024414, 3.2079248428344727, 2.641171932220459, 3.502934455871582, 3.3942010402679443, 3.515130043029785, 2.6842663288116455, 3.0942180156707764, 1.8084079027175903, 2.736666202545166, 3.3377816677093506, 1.8862732648849487, 2.753405809402466, 1.33198082447052, 1.8404146432876587, 2.2023115158081055, 4.216795921325684, 3.2064244747161865, 3.769320011138916, 2.5431947708129883, 4.016176700592041, 2.503594398498535, 2.52388334274292, 1.994135856628418, 2.69565486907959, 3.3377773761749268, 3.0961031913757324, 2.1991631984710693, 3.1051573753356934, 1.3089383840560913, 1.661965250968933, 2.9420318603515625, 2.6367056369781494, 2.1808204650878906, 2.641373872756958, 2.3778886795043945, 3.4972410202026367, 3.324949264526367, 2.5752477645874023, 1.7512215375900269, 2.466884136199951, 2.0903215408325195, 3.454118490219116, 3.415339231491089, 4.107842445373535, 3.5518980026245117, 2.299920082092285, 3.072316884994507, 3.3338844776153564, 1.9059799909591675, 2.5777788162231445, 2.2496771812438965, 2.942472457885742, 2.4819912910461426, 2.6713578701019287, 3.1208465099334717, 2.9757957458496094, 1.194007396697998, 3.7493388652801514, 2.2675085067749023, 2.2207412719726562, 2.3416953086853027, 1.426141619682312, 3.383244514465332, 3.120123863220215, 2.0543930530548096, 2.27555775642395, 2.381382942199707, 3.380251884460449, 3.8519718647003174, 3.939803123474121, 2.229145050048828, 2.51155424118042, 3.764399290084839, 3.7154531478881836, 2.245203971862793, 3.2805557250976562, 1.6496191024780273, 3.1663787364959717, 2.2179269790649414, 2.8596205711364746, 3.416121244430542, 2.4654126167297363, 1.671259880065918, 3.430511951446533, 2.780352830886841, 2.33640193939209, 1.9024187326431274, 4.071933269500732, 1.944723129272461, 2.4001760482788086, 2.1693968772888184, 3.6385467052459717, 1.3818159103393555, 2.282682418823242, 1.977431297302246, 2.9245193004608154, 1.7356616258621216, 2.8744900226593018, 2.899033784866333, 2.7850983142852783, 2.5416345596313477, 2.922717332839966, 0.302750825881958, 0.22963573038578033, 0.2771592140197754, 0.2648017108440399, 0.19178889691829681, 0.27860087156295776, 0.19095270335674286, 0.3250303268432617, 0.13233041763305664, 0.2181686908006668, 0.2305898219347, 0.204045832157135, 0.21428397297859192, 0.20259897410869598, 0.22137928009033203, 0.21589601039886475, 0.18253591656684875, 0.21188178658485413, 0.246474027633667, 0.22393310070037842, 0.22938428819179535, 0.2688411474227905, 0.18046779930591583, 0.21576270461082458, 0.20597097277641296, 0.29208385944366455, 0.2613319456577301, 0.2852407693862915, 0.17168018221855164, 0.17893581092357635, 0.22143514454364777, 0.24950926005840302, 0.26559045910835266, 0.2210017591714859, 0.28315988183021545, 0.17313136160373688, 0.18827684223651886, 0.17639118432998657, 0.12097868323326111, 0.23919296264648438, 0.29671886563301086, 0.22510965168476105, 0.23288238048553467, 0.22687110304832458, 0.2175580859184265, 0.2711157500743866, 0.2032129168510437, 0.2528938949108124, 0.1755729615688324, 0.20173899829387665, 0.1457444578409195, 0.22028420865535736, 0.24779357016086578, 0.2176518589258194, 0.18483471870422363, 0.1893693506717682, 0.2804555594921112, 0.26784005761146545, 0.16605615615844727, 0.21799349784851074, 0.2131703943014145, 0.2053716480731964, 0.21394453942775726, 0.2182161659002304, 0.1878058761358261, 0.24300555884838104, 0.16573843359947205, 0.24149875342845917, 0.2847614586353302, 0.21978652477264404, 0.32994282245635986, 0.23337489366531372, 0.1945471316576004, 0.20340874791145325, 0.27702319622039795, 0.1889871507883072, 0.21625234186649323, 0.15967856347560883, 0.2340882271528244, 0.27094170451164246, 0.21202629804611206, 0.20008273422718048, 0.23496222496032715, 0.1832849085330963, 0.23420056700706482, 0.2115984708070755, 0.20600314438343048, 0.28742098808288574, 0.18751628696918488, 0.20791234076023102, 0.17740067839622498, 0.22881481051445007, 0.16836532950401306, 0.1420164704322815, 0.1486644297838211, 0.2319091409444809, 0.20473849773406982, 0.2380983680486679, 0.2227359563112259, 0.25046131014823914, 0.20352384448051453, 0.19002099335193634, 0.14257121086120605, 0.26917028427124023, 0.26016196608543396, 0.1920510083436966, 0.21947261691093445, 0.21484656631946564, 0.2321041375398636, 0.17592090368270874, 0.24033454060554504, 0.2162245512008667, 0.17718105018138885, 0.2362937480211258, 0.20868046581745148, 0.23023982346057892, 0.19413116574287415, 0.19029368460178375, 0.23158858716487885, 0.21921774744987488, 0.15868926048278809, 0.19748954474925995, 0.1716776043176651, 0.23607507348060608, 0.1972958743572235, 0.22465476393699646, 0.19598975777626038, 0.23694920539855957, 0.26211386919021606, 0.2619253396987915, 0.19637353718280792, 0.28206026554107666, 0.22622539103031158, 0.19484782218933105, 0.2927427291870117, 0.17716561257839203, 0.2549073398113251, 0.23876029253005981, 0.23658353090286255, 0.237221822142601, 0.20821532607078552, 0.2156984657049179, 0.20482192933559418, 0.2191544622182846, 0.17844358086585999, 0.18617454171180725, 0.20895007252693176, 0.22615019977092743, 0.23408396542072296, 0.2550452649593353, 0.21594762802124023, 0.16875335574150085, 0.2537364661693573, 0.1829949915409088, 0.21143275499343872, 0.27815523743629456, 0.19545912742614746, 0.25787296891212463, 0.21861658990383148, 0.19146595895290375, 0.15407922863960266, 0.22048401832580566, 0.2546890676021576, 0.19970214366912842, 0.1881057173013687, 0.2674935460090637, 0.17882519960403442, 0.26270002126693726, 0.21004855632781982, 0.20556895434856415, 0.14917156100273132, 0.21284359693527222, 0.22989004850387573, 0.1641148179769516, 0.15947791934013367, 0.23742182552814484, 0.1928979605436325, 0.2178763896226883, 0.2120501697063446, 0.18825626373291016, 0.20377665758132935, 0.20039840042591095, 0.1953880339860916, 0.17625176906585693, 0.2591067850589752, 0.1391081064939499, 0.23338072001934052, 0.20640388131141663, 0.27190065383911133, 0.252606600522995, 0.20448210835456848, 0.23064811527729034, 0.19018065929412842, 0.1527414321899414, 0.21661138534545898, 0.2047056406736374, 0.2516585886478424, 0.2243475317955017, 0.2226121425628662, 0.204818457365036, 0.25093626976013184, 0.3217821419239044, 0.24361804127693176, 0.22156153619289398, 0.20272082090377808, 0.22296832501888275, 0.19307692348957062, 0.2482846975326538, 0.20311343669891357, 0.2532278895378113, 0.22999604046344757, 0.19256754219532013, 0.2610670328140259, 0.21128708124160767, 0.3239282965660095, 0.20990844070911407, 0.23231106996536255, 0.2294994443655014, 0.21367692947387695, 0.24669377505779266, 0.19753798842430115, 0.19400426745414734, 0.19874811172485352, 0.27774447202682495, 0.224715918302536, 0.19126278162002563, 0.23695813119411469, 0.19907298684120178, 0.19941097497940063, 0.22276996076107025, 0.21832187473773956, 0.23797576129436493, 0.2696480453014374, 0.15896503627300262, 0.2570819854736328, 0.25448891520500183, 0.15949365496635437, 0.2319057285785675, 0.2665235698223114, 0.20185378193855286, 0.20881694555282593, 0.18527613580226898, 0.2335415631532669, 0.18762771785259247, 0.1611555963754654, 0.23518916964530945, 0.21847404539585114, 0.22556263208389282, 0.1912037581205368, 0.21425281465053558, 0.22839248180389404, 0.24676577746868134, 0.1782049685716629, 0.19223275780677795, 0.22834888100624084, 0.17558619379997253, 0.18590793013572693, 0.21755221486091614, 0.21797722578048706, 0.18235738575458527, 0.26177966594696045, 0.2568410336971283, 0.21076194941997528, 0.1441861093044281, 0.20713317394256592, 0.21396510303020477, 0.16697879135608673, 0.22118113934993744, 0.21065065264701843, 0.22584515810012817, 0.1729816347360611, 0.22596007585525513, 0.21156646311283112, 0.2269953042268753, 0.2288646250963211, 0.1651184856891632, 0.19256919622421265, 0.25886186957359314, 0.2203538417816162, 0.2591809928417206, 0.24625931680202484, 0.21709269285202026, 0.26503390073776245, 0.18446528911590576, 0.2633252739906311, 0.19513384997844696, 0.20289424061775208, 0.2012646496295929, 0.16219660639762878, 0.2290564626455307, 0.17780743539333344, 0.2763834595680237, 0.21398158371448517, 0.2866504490375519, 0.2448149174451828, 0.27028170228004456, 0.16744430363178253, 0.22879865765571594, 0.21232540905475616, 0.2078874558210373, 1.2848727703094482, 2.2884840965270996, 2.2428383827209473, 2.9231362342834473, 2.181535243988037, 1.9530977010726929, 2.341679096221924, 1.7777814865112305, 2.5231425762176514, 2.9862747192382812, 1.9723637104034424, 1.991715908050537, 2.576181650161743, 2.136648416519165, 2.294901132583618, 1.9989941120147705, 2.7000527381896973, 2.7136645317077637, 2.7313365936279297, 1.4536997079849243, 3.196580171585083, 2.9534988403320312, 2.4339308738708496, 1.8846346139907837, 2.1865744590759277, 2.0132524967193604, 2.6688268184661865, 2.7081329822540283, 2.0018084049224854, 2.7243599891662598, 2.4931890964508057, 2.1094794273376465, 2.072073459625244, 2.0989766120910645, 1.5766204595565796, 2.00478458404541, 2.2221953868865967, 1.9736629724502563, 2.5080041885375977, 1.1977956295013428, 2.4883551597595215, 2.22983717918396, 2.956638813018799, 1.966500163078308, 2.6882083415985107, 2.260937213897705, 1.7798906564712524, 2.0678224563598633, 2.6283257007598877, 2.0329747200012207, 3.607760190963745, 3.302974224090576, 3.025726318359375, 3.466844320297241, 2.255082845687866, 2.4023802280426025, 3.4778218269348145, 3.316441774368286, 1.2078971862792969, 3.292816638946533, 2.047405242919922, 1.5745372772216797, 2.2309088706970215, 2.4781136512756348, 3.2600085735321045, 2.170097589492798, 1.782700777053833, 1.245805025100708, 2.1336708068847656, 1.8906530141830444, 2.0467963218688965, 2.294961452484131, 1.6346282958984375, 2.401257038116455, 1.9921232461929321, 2.516908884048462, 2.030667304992676, 2.6978700160980225, 1.833677887916565, 2.7235641479492188, 2.0118489265441895, 2.887284994125366, 2.7844913005828857, 2.9105818271636963, 2.168221950531006, 2.0608654022216797, 2.4992499351501465, 1.8061312437057495, 2.0569798946380615, 1.8800909519195557, 2.7131717205047607, 3.693423271179199, 2.2220232486724854, 1.625632643699646, 2.2256860733032227, 2.380021572113037, 2.062089443206787, 2.070706367492676, 1.6999821662902832, 2.7722725868225098, 1.6475251913070679, 1.7687193155288696, 2.4014716148376465, 3.411750078201294, 2.380214214324951, 1.3931347131729126, 1.8341981172561646, 2.3683786392211914, 3.3777053356170654, 3.3930840492248535, 2.1542673110961914, 1.588770866394043, 1.3732622861862183, 2.4666218757629395, 1.5441683530807495, 2.3819682598114014, 2.8788979053497314, 2.8090014457702637, 2.9840087890625, 3.520501136779785, 1.3222112655639648, 2.6925177574157715, 2.5094845294952393, 1.7718464136123657, 2.456552743911743, 2.890886068344116, 1.7861837148666382, 3.090885639190674, 1.7440202236175537, 3.0546658039093018, 2.6268603801727295, 2.405855417251587, 2.5359368324279785, 2.020662784576416, 2.832425355911255, 2.1354336738586426, 2.3472676277160645, 2.44809627532959, 3.470844030380249, 2.7121822834014893, 2.382333278656006, 2.4519968032836914, 1.676124095916748, 3.315791606903076, 1.7478796243667603, 1.451101303100586, 1.936967372894287, 1.828203797340393, 2.0506491661071777, 2.220930814743042, 1.609150767326355, 2.884143352508545, 1.6089597940444946, 2.1154885292053223, 3.2752349376678467, 2.064404010772705, 2.573626756668091, 1.79025137424469, 3.130913257598877, 2.319239854812622, 3.3076870441436768, 2.2857015132904053, 2.432058095932007, 2.360813617706299, 2.366886615753174, 2.0941383838653564, 2.315951108932495, 2.1353371143341064, 2.715745687484741, 2.265061378479004, 1.3869373798370361, 3.566093921661377, 1.8418715000152588, 2.2140440940856934, 2.2280397415161133, 1.9784109592437744, 2.1053590774536133, 1.2781777381896973, 2.5555033683776855, 2.2126810550689697, 1.8937562704086304, 2.614297389984131, 1.3920732736587524, 3.6430282592773438, 2.3260316848754883, 2.6701455116271973, 2.181321859359741, 1.9803205728530884, 2.144801139831543, 1.4086450338363647, 1.6633236408233643, 2.5684642791748047, 2.964650869369507, 2.7585654258728027, 1.4679861068725586, 2.5374581813812256, 1.493761420249939, 1.6483796834945679, 2.54799222946167, 2.0899250507354736, 2.5384674072265625, 1.528821349143982, 2.353532075881958, 2.241939067840576, 1.968294382095337, 2.737067222595215, 3.861055850982666, 3.3393828868865967, 2.1305360794067383, 1.0988775491714478, 1.810325026512146, 2.6940178871154785, 1.3926016092300415, 2.581354856491089, 2.019005298614502, 2.3200314044952393, 1.9849309921264648, 2.8693699836730957, 2.1093831062316895, 1.3301761150360107, 2.035896062850952, 1.91851007938385, 2.5921454429626465, 2.3242623805999756, 2.2921881675720215, 1.6461657285690308, 3.6475765705108643, 2.223393201828003, 2.187333583831787, 2.412647247314453, 2.3126778602600098, 1.1688162088394165, 1.7897379398345947, 4.071882247924805, 1.6351969242095947, 2.1051955223083496, 1.9000577926635742, 1.4742285013198853, 1.5135536193847656, 1.992984414100647, 2.2959301471710205, 2.2387337684631348, 2.188007354736328, 1.7813656330108643, 1.9765300750732422, 1.5820211172103882, 3.0481789112091064, 2.8897666931152344, 1.8279943466186523, 2.8903777599334717, 2.4270215034484863, 2.8823063373565674, 2.1025643348693848, 1.4835680723190308, 3.7518692016601562, 2.1590986251831055, 3.1219584941864014, 2.209061622619629, 1.7590601444244385, 3.1559441089630127, 2.1486825942993164, 2.442866086959839, 1.717022180557251, 2.1026153564453125, 3.5515782833099365, 1.861056923866272, 1.985693335533142, 3.1484482288360596, 1.806161642074585, 2.949998617172241, 2.0389788150787354, 3.377234697341919, 2.6072001457214355, 1.7070465087890625, 1.275268793106079, 1.7450937032699585, 1.9782243967056274, 2.7208333015441895, 2.52824068069458, 1.6973596811294556, 2.0557327270507812, 1.7287098169326782, 2.0119469165802, 2.5241072177886963, 2.650278329849243, 2.2909021377563477, 1.6599254608154297, 1.3827675580978394, 1.3042736053466797, 2.7898595333099365, 2.9027926921844482, 2.827068328857422, 1.6462637186050415, 3.3137199878692627, 2.965946674346924, 2.086027145385742, 3.2039928436279297, 3.726154088973999, 2.2652127742767334, 1.9248243570327759, 204.2834014892578, 37.05078125, 96.985595703125, 243.3695831298828, 210.8593292236328, 476.51397705078125, 144.79864501953125, 80.04983520507812, 176.3220672607422, 46.84075927734375, 161.2060546875, 129.82257080078125, 468.07373046875, 184.7086944580078, 166.91363525390625, 94.13406372070312, 76.7943115234375, 48.329681396484375, 275.9472351074219, 337.0980529785156, 206.56314086914062, 111.40548706054688, 56.6422119140625, 89.3397216796875, 132.97032165527344, 66.43116760253906, 149.843017578125, 430.0809631347656, 80.52422332763672, 161.7060089111328, 53.615291595458984, 173.01377868652344, 184.7643280029297, 141.9706268310547, 197.675537109375, 278.58953857421875, 35.35821533203125, 140.08120727539062, 108.47625732421875, 301.9764404296875, 312.4876403808594, 193.39122009277344, 181.0355682373047, 76.5372314453125, 61.64436340332031, 70.76107788085938, 190.34347534179688, 156.0496826171875, 59.846492767333984, 309.7660217285156, 300.8831481933594, 156.13751220703125, 178.61192321777344, 84.11608123779297, 340.02435302734375, 123.84579467773438, 57.59139633178711, 244.26925659179688, 254.4403076171875, 116.95916748046875, 48.469970703125, 225.47528076171875, 248.07855224609375, 262.5126953125, 188.9744415283203, 158.47802734375, 171.24229431152344, 184.7267608642578, 414.8802490234375, 244.6141357421875, 52.08816146850586, 40.87202072143555, 105.8416748046875, 103.29410552978516, 143.265869140625, 183.47488403320312, 122.59368896484375, 281.1202392578125, 90.49808502197266, 201.08853149414062, 157.0865936279297, 149.61599731445312, 394.6600036621094, 264.0027770996094, 49.08099365234375, 71.02005004882812, 112.763916015625, 159.01112365722656, 42.62258529663086, 187.0402374267578, 179.02099609375, 129.49314880371094, 178.8252716064453, 91.17547607421875, 37.60858154296875, 95.90898895263672, 37.73333740234375, 281.9739685058594, 135.37515258789062, 236.7245635986328, 292.15155029296875, 35.67734909057617, 360.5771484375, 208.8216094970703, 126.7030029296875, 100.05187225341797, 64.40839385986328, 213.88047790527344, 167.93017578125, 312.75592041015625, 307.0437316894531, 128.3002166748047, 101.50775146484375, 262.5981140136719, 169.81797790527344, 302.80560302734375, 297.2370300292969, 342.6115417480469, 41.4482421875, 39.04484558105469, 126.48517608642578, 211.40399169921875, 149.47911071777344, 108.5806884765625, 76.94281005859375, 335.5917053222656, 247.28260803222656, 236.67518615722656, 143.50421142578125, 381.88873291015625, 132.51040649414062, 142.6044921875, 204.75128173828125, 96.68701171875, 156.71299743652344, 286.3438720703125, 96.55109405517578, 114.04159545898438, 134.5299835205078, 65.10595703125, 71.3955078125, 191.6376495361328, 229.6156768798828, 216.61192321777344, 228.3417205810547, 170.7674560546875, 243.07403564453125, 185.9644317626953, 185.81866455078125, 277.3108215332031, 138.69786071777344, 258.60662841796875, 94.42705535888672, 43.73542022705078, 371.6791076660156, 132.07728576660156, 89.1590805053711, 265.6683654785156, 57.11115264892578, 189.1963653564453, 300.4335021972656, 62.920780181884766, 138.02557373046875, 71.72408294677734, 52.9505615234375, 324.8827819824219, 186.74212646484375, 224.96153259277344, 128.8538360595703, 64.71570587158203, 299.124755859375, 102.90682983398438, 97.57156372070312, 112.7179946899414, 64.65478515625, 195.90478515625, 70.5098876953125, 321.3526611328125, 66.94730377197266, 85.0936279296875, 65.70179748535156, 117.03165435791016, 188.98117065429688, 148.99032592773438, 48.824100494384766, 96.34651947021484, 95.57440185546875, 190.4159393310547, 333.9188537597656, 177.0868682861328, 123.64995574951172, 98.95098114013672, 54.33354949951172, 111.09598541259766, 123.39501953125, 135.77932739257812, 191.4453887939453, 47.21718978881836, 85.2952880859375, 148.35504150390625, 175.79339599609375, 237.0867919921875, 85.5286865234375, 141.27003479003906, 218.4877471923828, 102.16421508789062, 506.1578674316406, 138.601318359375, 365.7496643066406, 112.5799560546875, 228.8544464111328, 181.50889587402344, 245.992919921875, 190.5655059814453, 132.0565185546875, 214.92401123046875, 50.901737213134766, 292.813232421875, 64.78092956542969, 304.35357666015625, 230.7904052734375, 326.2784423828125, 151.91583251953125, 87.18663787841797, 29.68597412109375, 106.93826293945312, 124.57076263427734, 51.30793380737305, 72.66253662109375, 340.4725036621094, 152.2144317626953, 485.5159912109375, 256.93231201171875, 406.0777893066406, 142.64247131347656, 112.26290130615234, 205.1184844970703, 63.84423828125, 120.74620819091797, 69.55742645263672, 419.3729553222656, 105.1981201171875, 239.43582153320312, 173.091796875, 127.13115692138672, 84.84502410888672, 244.33973693847656, 74.31591796875, 180.83609008789062, 96.43511199951172, 421.5956115722656, 116.94483184814453, 43.794490814208984, 47.80012893676758, 140.67518615722656, 368.36920166015625, 177.988037109375, 241.9740447998047, 241.505615234375, 48.436767578125, 145.585205078125, 69.197998046875, 129.91041564941406, 396.4562683105469, 333.82244873046875, 37.68378448486328, 159.65185546875, 108.76409912109375, 127.02828216552734, 45.6550178527832, 166.32521057128906, 179.1110382080078, 271.390625, 96.85982513427734, 35.28338623046875, 151.63043212890625, 110.05352020263672, 119.0516586303711, 37.38979721069336, 36.536006927490234, 225.6177520751953, 112.2508544921875, 296.00982666015625, 132.79161071777344, 135.10226440429688, 43.63525390625, 155.42279052734375, 100.36995697021484, 525.003173828125, 45.633602142333984, 144.02532958984375, 155.07421875, 245.14776611328125, 195.85980224609375, 57.05178451538086, 144.9975128173828, 57.34130859375, 144.08773803710938, 439.3288269042969, 542.5166015625, 2.2795629501342773, 3.0498290061950684, 1.637105941772461, 1.9718587398529053, 2.7033495903015137, 4.433411598205566, 2.7643988132476807, 2.0243749618530273, 2.6131432056427, 3.031952142715454, 1.947352409362793, 2.615229368209839, 2.409663438796997, 2.0385541915893555, 2.896968364715576, 2.0271687507629395, 1.4296188354492188, 2.994013547897339, 2.503382682800293, 2.4909486770629883, 2.708766460418701, 1.8174546957015991, 1.169739842414856, 2.4785475730895996, 2.7588412761688232, 2.233001708984375, 2.34118390083313, 1.2929868698120117, 2.610203266143799, 3.1820013523101807, 3.618197441101074, 2.846324920654297, 2.1038618087768555, 3.281104326248169, 2.3630917072296143, 3.44292950630188, 2.5850882530212402, 3.440192461013794, 1.6977852582931519, 3.527029275894165, 2.318434000015259, 3.788886070251465, 1.1065359115600586, 3.118361711502075, 2.74308705329895, 2.3930299282073975, 2.5612587928771973, 2.2349019050598145, 2.0680060386657715, 3.5089638233184814, 1.8840481042861938, 1.9293395280838013, 1.5878705978393555, 3.097693681716919, 2.2763595581054688, 3.7974462509155273, 2.320064067840576, 2.5301177501678467, 2.112595558166504, 2.9709630012512207, 1.8008313179016113, 2.344115972518921, 1.9256778955459595, 2.7664897441864014, 2.5995802879333496, 2.289337396621704, 3.074376106262207, 1.7529391050338745, 2.042239189147949, 2.9023661613464355, 2.9862773418426514, 2.588372230529785, 3.534670829772949, 3.5890350341796875, 2.507831335067749, 2.613968849182129, 2.9846317768096924, 3.494105815887451, 2.240105628967285, 3.300839424133301, 3.315446615219116, 3.7887449264526367, 3.408066987991333, 2.691112518310547, 3.106389045715332, 2.341249942779541, 1.9496852159500122, 2.3153982162475586, 3.6658337116241455, 2.2735414505004883, 3.8192222118377686, 3.2692949771881104, 1.8455393314361572, 2.8203976154327393, 2.5710365772247314, 3.3104424476623535, 2.3807268142700195, 1.9889041185379028, 1.4039654731750488, 2.2999937534332275, 1.4107885360717773, 2.41711688041687, 1.8130309581756592, 2.675457000732422, 2.2024571895599365, 2.847662925720215, 2.667325496673584, 2.723790168762207, 2.8562474250793457, 1.5207476615905762, 1.7946709394454956, 2.7361700534820557, 2.845515012741089, 2.760016679763794, 2.001612663269043, 2.4966652393341064, 3.627427339553833, 2.235999345779419, 1.74590003490448, 1.915200114250183, 2.4627909660339355, 1.4429562091827393, 2.871530055999756, 1.8963994979858398, 3.376533031463623, 2.2246551513671875, 2.3534727096557617, 3.55966854095459, 1.4456374645233154, 1.6356017589569092, 2.285294771194458, 3.261902332305908, 2.464824676513672, 2.0829904079437256, 3.159634590148926, 1.8324731588363647, 2.8154537677764893, 1.3464984893798828, 2.272294282913208, 3.2433958053588867, 1.8805747032165527, 4.14526891708374, 2.2596311569213867, 4.07283878326416, 1.8965792655944824, 1.0530853271484375, 2.721918821334839, 3.8011791706085205, 1.7004097700119019, 2.2142157554626465, 2.5181562900543213, 2.1970415115356445, 2.1613645553588867, 1.6568306684494019, 1.8739670515060425, 2.627207040786743, 2.3592543601989746, 3.88525128364563, 1.9588881731033325, 2.5958166122436523, 4.055970191955566, 2.3756744861602783, 2.3004868030548096, 2.708667755126953, 3.1804614067077637, 2.724668025970459, 2.5789871215820312, 3.089822292327881, 1.4565666913986206, 2.8931567668914795, 2.495919942855835, 2.7587175369262695, 2.53756046295166, 1.9557946920394897, 2.3188774585723877, 2.6776721477508545, 2.666192054748535, 4.153827667236328, 1.8067556619644165, 2.9560933113098145, 3.363386869430542, 3.2524211406707764, 2.450335741043091, 1.8925046920776367, 2.3959054946899414, 1.5550354719161987, 1.3954440355300903, 3.3482983112335205, 2.1027560234069824, 3.023137092590332, 3.20046329498291, 2.8767426013946533, 3.473788261413574, 3.115330696105957, 2.558854341506958, 2.5527946949005127, 2.943450450897217, 3.6308517456054688, 2.314762830734253, 3.0823473930358887, 1.6208313703536987, 2.144157648086548, 2.94860577583313, 2.4786794185638428, 1.9546314477920532, 2.2919561862945557, 2.6689999103546143, 2.9690487384796143, 2.431645393371582, 2.4324824810028076, 2.3962018489837646, 4.012556552886963, 2.921748638153076, 2.6765828132629395, 3.1999566555023193, 3.5594451427459717, 3.6266233921051025, 3.404332399368286, 2.3493471145629883, 1.4358646869659424, 2.8338463306427, 2.5966789722442627, 2.4718589782714844, 2.857959032058716, 1.0589714050292969, 2.6320831775665283, 2.5116701126098633, 2.5169248580932617, 2.416891098022461, 2.292191505432129, 1.8871759176254272, 2.256286144256592, 1.8933686017990112, 2.0388691425323486, 3.3721020221710205, 3.3523552417755127, 2.023989677429199, 3.1096508502960205, 2.4946365356445312, 2.3268496990203857, 2.192491054534912, 2.039952278137207, 3.844926118850708, 2.7705299854278564, 2.9471447467803955, 2.0116429328918457, 2.539496421813965, 3.2278900146484375, 2.0127973556518555, 1.6388062238693237, 2.060262680053711, 3.3676159381866455, 3.2186031341552734, 2.1940319538116455, 3.154446840286255, 2.96164608001709, 3.3360018730163574, 2.7400565147399902, 2.6751153469085693, 3.5318493843078613, 2.9568588733673096, 1.8178585767745972, 2.1189870834350586, 4.032496452331543, 2.7855045795440674, 3.6808853149414062, 1.5773786306381226, 1.7770968675613403, 1.7981842756271362, 2.096207618713379, 1.2435511350631714, 2.698702335357666, 2.0639123916625977, 2.189568519592285, 2.086383104324341, 3.3078625202178955, 2.03780460357666, 2.6446661949157715, 1.9367971420288086, 2.8537685871124268, 3.178370237350464, 1.9514700174331665, 3.4802584648132324, 3.6229772567749023, 3.0165531635284424, 2.1484384536743164, 2.725999116897583, 2.6213576793670654, 4.046618461608887, 2.097566843032837, 1.6763006448745728, 1.9825674295425415, 2.7695305347442627, 2.409029722213745, 3.272198438644409, 1.9504733085632324, 3.165379762649536, 2.432788372039795, 2.9623444080352783, 3.4896059036254883, 0.23922842741012573, 0.17958968877792358, 0.2566034197807312, 0.18403121829032898, 0.25116273760795593, 0.27238067984580994, 0.2110159695148468, 0.18027129769325256, 0.26892995834350586, 0.24288299679756165, 0.2569414973258972, 0.22927050292491913, 0.23966670036315918, 0.1842225342988968, 0.2622317969799042, 0.2563353180885315, 0.20051215589046478, 0.19643622636795044, 0.20031629502773285, 0.26088157296180725, 0.15827445685863495, 0.20230942964553833, 0.19280000030994415, 0.21594226360321045, 0.2004605382680893, 0.18937383592128754, 0.2753344178199768, 0.16390666365623474, 0.1621735394001007, 0.17380768060684204, 0.18581798672676086, 0.17512665688991547, 0.2644994556903839, 0.20874154567718506, 0.2610621750354767, 0.2732924818992615, 0.20651210844516754, 0.2250499725341797, 0.2542990446090698, 0.16582369804382324, 0.27648571133613586, 0.25733888149261475, 0.22816844284534454, 0.15739522874355316, 0.2632395625114441, 0.23084871470928192, 0.24718859791755676, 0.21277493238449097, 0.2246459722518921, 0.2514038383960724, 0.21497610211372375, 0.12972553074359894, 0.237031951546669, 0.202654629945755, 0.24421149492263794, 0.20866020023822784, 0.18633714318275452, 0.29127222299575806, 0.18177926540374756, 0.28781771659851074, 0.23677372932434082, 0.19640052318572998, 0.16946303844451904, 0.18622639775276184, 0.20529145002365112, 0.23059852421283722, 0.300387978553772, 0.2185649871826172, 0.22658808529376984, 0.1727963536977768, 0.17118258774280548, 0.2503229081630707, 0.20658749341964722, 0.2112892121076584, 0.2616952657699585, 0.2502098083496094, 0.16505897045135498, 0.2653537392616272, 0.23068220913410187, 0.22160598635673523, 0.2315724641084671, 0.2336132526397705, 0.23063182830810547, 0.22572846710681915, 0.2287772297859192, 0.2054658979177475, 0.23606644570827484, 0.236520916223526, 0.19249582290649414, 0.19973742961883545, 0.1889120638370514, 0.1828775703907013, 0.23062770068645477, 0.19874419271945953, 0.25788700580596924, 0.23447535932064056, 0.1842094361782074, 0.21816079318523407, 0.19767649471759796, 0.20566803216934204, 0.18383625149726868, 0.1290019452571869, 0.24765467643737793, 0.18870647251605988, 0.29176029562950134, 0.18775205314159393, 0.22276411950588226, 0.15026003122329712, 0.2564244270324707, 0.21095459163188934, 0.23655688762664795, 0.17679718136787415, 0.28729650378227234, 0.22098100185394287, 0.1877601146697998, 0.22216598689556122, 0.22882938385009766, 0.20057623088359833, 0.23423250019550323, 0.22107179462909698, 0.22683186829090118, 0.2475423365831375, 0.21734336018562317, 0.1831475794315338, 0.23507653176784515, 0.2574880123138428, 0.22575032711029053, 0.19883209466934204, 0.21179798245429993, 0.18066442012786865, 0.2583203911781311, 0.239792138338089, 0.23473896086215973, 0.22148986160755157, 0.19592347741127014, 0.21668373048305511, 0.18006081879138947, 0.25032544136047363, 0.21528184413909912, 0.2740156054496765, 0.2550303637981415, 0.2031816691160202, 0.2843528091907501, 0.18801242113113403, 0.23063001036643982, 0.17540770769119263, 0.2144894152879715, 0.23391631245613098, 0.21947376430034637, 0.16567985713481903, 0.2447364777326584, 0.2682332992553711, 0.14788275957107544, 0.2325756847858429, 0.25953373312950134, 0.15491533279418945, 0.22982454299926758, 0.2128564715385437, 0.2213594764471054, 0.1774040162563324, 0.24092411994934082, 0.2313268482685089, 0.1990899294614792, 0.214354008436203, 0.3061234951019287, 0.2049819678068161, 0.2286883443593979, 0.26952144503593445, 0.25283753871917725, 0.24061377346515656, 0.21899600327014923, 0.21804682910442352, 0.23461781442165375, 0.18944095075130463, 0.2779063880443573, 0.2109822779893875, 0.19137173891067505, 0.17034777998924255, 0.1791246384382248, 0.22393670678138733, 0.21167416870594025, 0.2119247317314148, 0.14920391142368317, 0.167347714304924, 0.1984032541513443, 0.2972232401371002, 0.23984234035015106, 0.2475450485944748, 0.28862497210502625, 0.19103379547595978, 0.14994797110557556, 0.18630753457546234, 0.1990528106689453, 0.2843095064163208, 0.19452296197414398, 0.23093606531620026, 0.22922317683696747, 0.22274062037467957, 0.2231266349554062, 0.23285233974456787, 0.1949133276939392, 0.18789620697498322, 0.2502713203430176, 0.1705336570739746, 0.18987543880939484, 0.1679331213235855, 0.240614652633667, 0.19053132832050323, 0.28456854820251465, 0.2367527335882187, 0.1279781311750412, 0.2268143743276596, 0.2564027011394501, 0.21664820611476898, 0.256744384765625, 0.19366542994976044, 0.21052058041095734, 0.2286231517791748, 0.26350313425064087, 0.19760596752166748, 0.21918053925037384, 0.16823077201843262, 0.27395039796829224, 0.22052240371704102, 0.22155757248401642, 0.23687468469142914, 0.21513350307941437, 0.1761055886745453, 0.1638302505016327, 0.19728252291679382, 0.20384809374809265, 0.21183791756629944, 0.19990050792694092, 0.25305283069610596, 0.18301084637641907, 0.22476020455360413, 0.2540697157382965, 0.23739522695541382, 0.2703206539154053, 0.19306205213069916, 0.24100501835346222, 0.19615332782268524, 0.21961729228496552, 0.2248672991991043, 0.2316645234823227, 0.2476179003715515, 0.17200763523578644, 0.2630181610584259, 0.2452654391527176, 0.22176599502563477, 0.18922922015190125, 0.23309248685836792, 0.23935018479824066, 0.18724863231182098, 0.2640742361545563, 0.2327050417661667, 0.19513177871704102, 0.2104233056306839, 0.23702235519886017, 0.22924454510211945, 0.25134825706481934, 0.21657708287239075, 0.17738594114780426, 0.1425161510705948, 0.22544805705547333, 0.24542850255966187, 0.18425719439983368, 0.3365626335144043, 0.19045068323612213, 0.14946869015693665, 0.2140059620141983, 0.24975241720676422, 0.19684848189353943, 0.24284884333610535, 0.2584505081176758, 0.18177497386932373, 0.14245526492595673, 0.1897285282611847, 0.2183648645877838, 0.13979922235012054, 0.1862771064043045, 0.278402179479599, 0.26210924983024597, 0.23987425863742828, 0.265118807554245, 0.23198559880256653, 0.1883438378572464, 0.22849096357822418, 0.2486410290002823, 0.18402428925037384, 0.13183879852294922, 0.17682133615016937, 0.2480427473783493, 0.21905803680419922, 0.27613818645477295, 0.23552703857421875, 0.20341160893440247, 0.20580583810806274, 0.22987449169158936, 0.22964903712272644, 1.7828811407089233, 2.990929126739502, 2.721787691116333, 4.395839691162109, 1.644952654838562, 3.0668840408325195, 1.572745680809021, 1.5751938819885254, 1.4675918817520142, 3.111011266708374, 2.1162471771240234, 3.5725350379943848, 1.9505081176757812, 2.1648454666137695, 1.4861587285995483, 1.7700392007827759, 2.1775777339935303, 2.306347370147705, 1.669523000717163, 1.5284448862075806, 2.6669280529022217, 2.734454393386841, 2.311528444290161, 2.148768663406372, 2.5886595249176025, 2.4885001182556152, 3.662893295288086, 2.31968355178833, 2.39113450050354, 2.381783962249756, 2.0450472831726074, 1.8134820461273193, 2.5454013347625732, 1.8295754194259644, 3.379349946975708, 3.0012195110321045, 2.9806621074676514, 2.2540717124938965, 3.527315616607666, 3.0850212574005127, 1.9113689661026, 2.3066458702087402, 1.9930384159088135, 1.9798463582992554, 1.6934814453125, 2.4704644680023193, 2.768939256668091, 1.8924179077148438, 3.3209316730499268, 1.4004970788955688, 2.2426388263702393, 1.337640643119812, 1.9711920022964478, 3.817780017852783, 3.001469373703003, 2.529175281524658, 2.573652982711792, 2.0875625610351562, 2.711993455886841, 1.6990102529525757, 2.42738938331604, 2.5918004512786865, 2.799896240234375, 1.9130899906158447, 3.0556488037109375, 1.847253680229187, 2.4889752864837646, 1.9778192043304443, 2.3876919746398926, 1.8046009540557861, 3.3478710651397705, 3.0337440967559814, 2.7750136852264404, 2.3790805339813232, 1.9008594751358032, 2.442474842071533, 2.078139305114746, 3.023430347442627, 2.4913699626922607, 1.403739333152771, 2.5176637172698975, 1.814136028289795, 2.349581241607666, 2.306244373321533, 2.194568634033203, 3.0131444931030273, 2.5718016624450684, 2.6369409561157227, 1.7679946422576904, 1.7906075716018677, 3.068997621536255, 2.0273196697235107, 3.469594955444336, 1.9485610723495483, 2.039515495300293, 1.7385692596435547, 1.7067136764526367, 2.859121084213257, 1.46172297000885, 2.4956297874450684, 2.4390645027160645, 2.97839617729187, 2.8721885681152344, 1.7629766464233398, 1.5577882528305054, 2.3520898818969727, 2.240126848220825, 2.526951789855957, 2.08535099029541, 1.918143630027771, 2.2639987468719482, 2.5601048469543457, 1.8370640277862549, 2.96502423286438, 1.2570542097091675, 2.8139262199401855, 1.511111855506897, 1.948061227798462, 3.1736514568328857, 1.6256725788116455, 3.003833770751953, 1.6178069114685059, 2.2159342765808105, 2.164027452468872, 2.9328160285949707, 1.8665642738342285, 1.8507295846939087, 2.5846800804138184, 2.6837856769561768, 2.0592427253723145, 2.553401231765747, 2.4997270107269287, 2.356372356414795, 2.132347583770752, 1.3546117544174194, 1.7564769983291626, 1.986575722694397, 1.6980904340744019, 2.0551486015319824, 3.0212390422821045, 3.249945640563965, 2.0680065155029297, 2.0548110008239746, 2.5818943977355957, 1.5991244316101074, 3.3117969036102295, 3.1496002674102783, 2.5403170585632324, 2.011810064315796, 1.9095373153686523, 2.7052206993103027, 2.7051613330841064, 2.9461300373077393, 1.7277255058288574, 2.8944504261016846, 2.8892292976379395, 2.725639820098877, 1.2901403903961182, 1.444761872291565, 2.362191677093506, 1.9253534078598022, 2.951125383377075, 1.6606861352920532, 3.225537061691284, 2.2826759815216064, 3.8962035179138184, 1.843904972076416, 2.5764389038085938, 2.0809195041656494, 2.3055410385131836, 1.6667314767837524, 2.488152503967285, 1.8926467895507812, 2.1321945190429688, 2.2047643661499023, 2.7841503620147705, 1.9506475925445557, 2.7727789878845215, 2.7922427654266357, 2.227228879928589, 3.1560235023498535, 1.8764410018920898, 2.08724308013916, 1.8192962408065796, 1.8216381072998047, 1.917486548423767, 1.5972505807876587, 2.4389889240264893, 2.4622859954833984, 3.367324113845825, 1.7771471738815308, 2.5011279582977295, 2.22489595413208, 3.414097785949707, 2.114889621734619, 2.578914165496826, 2.2386322021484375, 2.2172181606292725, 3.030357837677002, 2.214435338973999, 2.095428943634033, 2.9430248737335205, 1.6143548488616943, 1.7733944654464722, 2.427424192428589, 2.6090636253356934, 1.3261141777038574, 2.6403825283050537, 2.3068902492523193, 3.0394394397735596, 1.7683557271957397, 1.9585694074630737, 2.2478902339935303, 2.9157021045684814, 1.1974693536758423, 3.288853645324707, 2.7838528156280518, 2.5267651081085205, 3.351966142654419, 1.4703463315963745, 2.1250295639038086, 3.0043869018554688, 2.9025073051452637, 1.855123519897461, 2.12323260307312, 2.8200578689575195, 2.6332061290740967, 2.107299327850342, 1.6635475158691406, 3.930433988571167, 1.7902113199234009, 1.5514719486236572, 3.3855223655700684, 1.829637050628662, 1.6140151023864746, 2.619413137435913, 2.564187526702881, 2.069685935974121, 2.409271240234375, 2.5107955932617188, 2.0376341342926025, 2.360032081604004, 1.4989242553710938, 1.976169228553772, 2.5205931663513184, 2.3745391368865967, 3.920111894607544, 1.61468505859375, 2.183385133743286, 3.164154052734375, 2.72324275970459, 2.29875111579895, 2.7569284439086914, 2.7162392139434814, 2.9456470012664795, 2.0707955360412598, 1.7159661054611206, 2.454942464828491, 4.721664905548096, 3.1211483478546143, 2.813380002975464, 2.521787166595459, 2.810412883758545, 1.9471737146377563, 2.6173558235168457, 3.177051305770874, 1.9383758306503296, 3.18869948387146, 2.8818938732147217, 2.362380266189575, 3.8966622352600098, 1.969442367553711, 1.8076854944229126, 2.844989061355591, 2.113400936126709, 2.750408887863159, 1.5479007959365845, 1.9734166860580444, 2.476047992706299, 3.1966638565063477, 2.7970402240753174, 1.7893307209014893, 1.6188207864761353, 2.967421770095825, 2.2800111770629883, 2.010493516921997, 3.1660492420196533, 2.553056001663208, 2.9297611713409424, 2.9941799640655518, 3.2671802043914795, 2.768494129180908, 2.434887409210205, 3.657680034637451, 2.390519618988037, 3.1128323078155518, 2.25679874420166, 2.965961217880249, 1.263753890991211, 2.230118751525879, 353.8162536621094, 83.2911148071289, 377.2574157714844, 111.21234130859375, 252.73294067382812, 411.2613525390625, 282.77899169921875, 118.00444793701172, 338.3433532714844, 317.5933837890625, 194.116943359375, 217.2552947998047, 282.0174560546875, 311.72021484375, 40.9666748046875, 311.60797119140625, 216.3466339111328, 171.47201538085938, 154.49127197265625, 332.7806091308594, 106.61827850341797, 50.35952377319336, 227.83799743652344, 223.2566375732422, 175.39964294433594, 108.05496978759766, 93.08110809326172, 303.1819763183594, 48.037353515625, 58.06243896484375, 161.2660675048828, 462.7021789550781, 236.36129760742188, 230.2923583984375, 307.4134216308594, 253.72042846679688, 72.67729949951172, 180.5437469482422, 98.95673370361328, 458.322998046875, 54.73944091796875, 435.7698974609375, 206.7329864501953, 56.675682067871094, 416.6319580078125, 138.0666046142578, 278.4953918457031, 252.9576873779297, 31.0743408203125, 456.1817932128906, 273.613525390625, 204.0215606689453, 40.08050537109375, 259.50360107421875, 236.52023315429688, 245.19981384277344, 223.9495849609375, 193.5613250732422, 119.48424530029297, 52.83570098876953, 116.18695068359375, 192.6490936279297, 81.69589233398438, 142.5517578125, 52.955135345458984, 148.81980895996094, 181.6517333984375, 401.76593017578125, 71.8753662109375, 507.3587646484375, 232.31756591796875, 84.69463348388672, 63.049560546875, 42.87078857421875, 252.10009765625, 134.37950134277344, 168.3701171875, 124.51412200927734, 90.7194595336914, 54.1295166015625, 40.51715087890625, 135.322509765625, 334.2078552246094, 156.09799194335938, 301.38226318359375, 394.7314453125, 201.60804748535156, 59.69889450073242, 439.3190002441406, 127.46551513671875, 216.57188415527344, 352.2069396972656, 185.0637969970703, 429.6998291015625, 76.69813537597656, 177.21205139160156, 61.0838623046875, 40.5863037109375, 256.89947509765625, 175.212646484375, 152.4464569091797, 237.3153533935547, 57.30435562133789, 113.94806671142578, 288.66473388671875, 81.4620132446289, 436.7581787109375, 289.1572265625, 74.782470703125, 129.94473266601562, 184.25540161132812, 145.80224609375, 410.3505859375, 253.0860137939453, 301.53839111328125, 264.7324523925781, 100.38390350341797, 295.3486633300781, 99.09845733642578, 156.49700927734375, 62.29443359375, 71.2579345703125, 121.41163635253906, 123.56084442138672, 162.6934814453125, 233.68194580078125, 252.48204040527344, 78.14642333984375, 108.11825561523438, 120.2175521850586, 79.528564453125, 261.8095703125, 112.04443359375, 267.52197265625, 159.3197021484375, 159.27264404296875, 327.1511535644531, 187.87294006347656, 249.4329376220703, 98.87353515625, 242.97393798828125, 124.36949157714844, 116.50279235839844, 96.642578125, 121.13721466064453, 72.81475830078125, 104.1696548461914, 166.9462127685547, 155.8505401611328, 196.09793090820312, 260.5947570800781, 174.0625, 162.90484619140625, 177.2601776123047, 85.61517333984375, 102.81976318359375, 440.0226135253906, 360.8367004394531, 148.81060791015625, 190.38409423828125, 33.14715576171875, 93.583251953125, 140.702880859375, 264.209228515625, 42.067138671875, 229.73350524902344, 95.82718658447266, 128.54449462890625, 212.80577087402344, 106.95532989501953, 376.98345947265625, 158.2181396484375, 97.0986099243164, 53.23682403564453, 334.2234191894531, 37.9105224609375, 293.24810791015625, 103.04133605957031, 166.5565643310547, 137.7763671875, 157.9164276123047, 103.1943359375, 303.39111328125, 175.87249755859375, 82.55390167236328, 71.59709167480469, 313.8031311035156, 407.8209228515625, 424.5685729980469, 147.22654724121094, 131.2410888671875, 106.64886474609375, 83.39289093017578, 171.49945068359375, 141.49151611328125, 683.5098876953125, 333.11553955078125, 129.70750427246094, 78.75772094726562, 178.75804138183594, 203.42160034179688, 112.3494873046875, 84.05229187011719, 407.3722839355469, 281.3046875, 173.20372009277344, 47.54638671875, 273.3683776855469, 352.29742431640625, 151.08892822265625, 191.3157958984375, 366.9328308105469, 412.83428955078125, 73.81697845458984, 172.32180786132812, 230.38340759277344, 335.9159240722656, 420.2093505859375, 110.35558319091797, 141.57530212402344, 75.05233001708984, 134.28143310546875, 145.503173828125, 266.34136962890625, 287.5483703613281, 50.67919921875, 147.21786499023438, 112.98628997802734, 324.3803405761719, 133.53546142578125, 196.5046844482422, 86.7689208984375, 283.6291198730469, 180.54112243652344, 147.98291015625, 213.0409393310547, 172.67002868652344, 35.172454833984375, 129.2704315185547, 270.3131408691406, 60.086814880371094, 142.31419372558594, 291.14166259765625, 82.2452163696289, 95.46710968017578, 81.16384887695312, 291.6693115234375, 105.64045715332031, 141.75369262695312, 175.55218505859375, 178.1926727294922, 179.74612426757812, 205.17987060546875, 63.93182373046875, 219.89425659179688, 345.5633544921875, 326.2826232910156, 105.5793228149414, 94.79792785644531, 91.19193267822266, 115.51130676269531, 255.5834503173828, 87.5634765625, 58.3928108215332, 187.34426879882812, 127.15677642822266, 155.8468780517578, 343.13336181640625, 145.58880615234375, 366.4231872558594, 390.9650573730469, 167.1287841796875, 96.1187515258789, 173.6910858154297, 278.7904357910156, 65.886962890625, 324.27801513671875, 474.82733154296875, 166.243896484375, 74.81852722167969, 93.9134521484375, 124.0992431640625, 158.8544464111328, 405.4210205078125, 117.72765350341797, 68.13847351074219, 226.681396484375, 301.4694519042969, 186.11212158203125, 154.2723388671875, 92.59065246582031, 417.5955505371094, 171.17710876464844, 133.51568603515625, 236.81103515625, 320.18621826171875, 122.9266357421875, 350.4750061035156, 236.33799743652344, 312.4469299316406, 2.0169806480407715, 2.812150239944458, 1.9498416185379028, 3.4933996200561523, 3.2193212509155273, 2.5338428020477295, 1.7447004318237305, 2.628859758377075, 3.0344974994659424, 1.8377561569213867, 3.5121798515319824, 4.029929161071777, 2.598038911819458, 2.5192582607269287, 4.330739974975586, 2.71950626373291, 2.70835018157959, 2.3321921825408936, 2.625063419342041, 2.5296401977539062, 1.3588237762451172, 2.9349288940429688, 2.698052406311035, 3.48154354095459, 2.4014930725097656, 3.972168445587158, 2.9833667278289795, 2.660351514816284, 3.6751720905303955, 2.41434383392334, 2.21099591255188, 2.2515273094177246, 1.7479523420333862, 3.36454701423645, 1.8864927291870117, 4.690524101257324, 3.3294286727905273, 1.9691047668457031, 2.9823644161224365, 2.38657283782959, 2.447842597961426, 2.806400775909424, 1.5942474603652954, 2.7138912677764893, 1.992372989654541, 3.827653169631958, 3.114140272140503, 2.2625300884246826, 1.657692790031433, 1.8938512802124023, 2.951472043991089, 2.1069211959838867, 1.675684928894043, 3.760024309158325, 3.014662981033325, 2.596647262573242, 2.479135036468506, 3.2704484462738037, 2.377436399459839, 3.122098922729492, 1.9132698774337769, 2.585507869720459, 2.326207160949707, 3.78497314453125, 3.320307493209839, 3.2119572162628174, 1.9897011518478394, 1.5903137922286987, 2.124912977218628, 2.1036500930786133, 3.2815263271331787, 2.0067968368530273, 3.4746322631835938, 3.5150206089019775, 2.9701759815216064, 2.8099071979522705, 2.8217265605926514, 2.7261576652526855, 3.353802442550659, 2.45569109916687, 2.425482988357544, 2.3912782669067383, 2.2652692794799805, 3.7660255432128906, 2.118466377258301, 3.336088180541992, 2.27835750579834, 2.958745002746582, 1.8422727584838867, 2.3768930435180664, 1.9435415267944336, 2.7635204792022705, 2.3446006774902344, 2.506760597229004, 1.652443766593933, 2.133690357208252, 1.7322447299957275, 2.0682592391967773, 2.4400970935821533, 2.4979748725891113, 1.6777070760726929, 2.113081932067871, 2.4874985218048096, 2.1397924423217773, 3.120654821395874, 1.6781339645385742, 2.655566453933716, 3.3114254474639893, 2.8171510696411133, 3.5378522872924805, 3.655306577682495, 1.9725273847579956, 2.1975626945495605, 3.1285829544067383, 3.751866340637207, 2.102689504623413, 3.271479368209839, 2.573296546936035, 3.1541779041290283, 2.0377206802368164, 3.1191320419311523, 3.249833106994629, 3.9834988117218018, 1.757800817489624, 2.6000664234161377, 2.5248823165893555, 2.431232452392578, 1.6798964738845825, 3.130031108856201, 3.7180583477020264, 2.0560598373413086, 2.8685319423675537, 2.4711103439331055, 2.236189842224121, 1.758134365081787, 2.836602210998535, 2.4173617362976074, 1.7672628164291382, 3.211989164352417, 3.0663082599639893, 3.1947174072265625, 1.7857688665390015, 2.139270067214966, 3.53470778465271, 2.8482890129089355, 3.165039539337158, 2.5070695877075195, 2.071885108947754, 2.268785238265991, 2.7230331897735596, 1.9808008670806885, 2.5659210681915283, 1.8974497318267822, 1.9301425218582153, 2.329141616821289, 3.1617634296417236, 2.4626762866973877, 2.930755138397217, 2.676467180252075, 3.5106828212738037, 1.8218052387237549, 2.4445254802703857, 1.8120903968811035, 2.1330575942993164, 1.8193435668945312, 3.8803112506866455, 1.6676567792892456, 3.1113293170928955, 2.8570454120635986, 2.829665422439575, 2.647310733795166, 2.6380417346954346, 3.919165849685669, 1.900370717048645, 3.197859525680542, 2.111579418182373, 2.494900703430176, 2.758471727371216, 1.7558960914611816, 2.5108883380889893, 1.1622636318206787, 1.8788344860076904, 3.189236879348755, 2.01784610748291, 2.179828405380249, 2.8349809646606445, 3.080521821975708, 2.766538143157959, 2.4168519973754883, 3.4583423137664795, 3.1532585620880127, 4.088147163391113, 3.167556047439575, 2.488062858581543, 2.7279138565063477, 2.222547769546509, 2.92877197265625, 1.5040138959884644, 2.3127174377441406, 2.2432260513305664, 1.4456760883331299, 3.1058592796325684, 3.3819990158081055, 2.5911591053009033, 1.6592903137207031, 3.136990785598755, 2.533646583557129, 2.44630765914917, 1.79812490940094, 2.3991308212280273, 2.623704671859741, 2.7835934162139893, 1.5855401754379272, 2.4175825119018555, 2.64734148979187, 3.8830649852752686, 1.0759536027908325, 2.6355035305023193, 2.993107795715332, 2.759594678878784, 3.292292594909668, 3.727503538131714, 3.4514265060424805, 3.167363166809082, 2.114487648010254, 1.6934843063354492, 3.3368139266967773, 1.801869511604309, 2.238905906677246, 1.7011653184890747, 2.6817924976348877, 2.4578824043273926, 2.2061376571655273, 2.6142027378082275, 3.567519426345825, 2.606358528137207, 2.3582866191864014, 2.5537543296813965, 2.0841245651245117, 2.4972774982452393, 1.8340386152267456, 1.6561977863311768, 3.0775671005249023, 1.8443523645401, 3.151510000228882, 2.3423147201538086, 2.516810417175293, 2.962536573410034, 1.4731839895248413, 2.7573654651641846, 2.2213830947875977, 2.09897518157959, 2.586657762527466, 1.9835768938064575, 1.7072794437408447, 3.167742967605591, 2.068603992462158, 3.798569917678833, 2.2279481887817383, 2.146592378616333, 2.388951301574707, 3.001568555831909, 3.1393096446990967, 2.4079408645629883, 4.307854652404785, 1.9326081275939941, 3.36327862739563, 2.7770955562591553, 2.791131019592285, 2.927659273147583, 3.993699312210083, 2.423733711242676, 3.0948173999786377, 1.914713978767395, 2.6422741413116455, 3.504603385925293, 4.056586742401123, 3.490542411804199, 2.782499074935913, 2.999652147293091, 2.753852128982544, 2.3313443660736084, 3.5904738903045654, 2.612177610397339, 2.9245402812957764, 3.2787933349609375, 4.1236748695373535, 3.5602166652679443, 2.148167610168457, 3.105013370513916, 2.000565528869629, 4.075648307800293, 2.1500744819641113, 2.3171091079711914, 2.336276054382324, 3.0863866806030273, 2.157958984375, 2.8768293857574463, 3.0772430896759033, 2.2365715503692627, 0.24976886808872223, 0.1764555275440216, 0.19770585000514984, 0.20643596351146698, 0.18934623897075653, 0.20229247212409973, 0.19413988292217255, 0.20363961160182953, 0.2392122745513916, 0.18581877648830414, 0.21810758113861084, 0.2623969614505768, 0.18838591873645782, 0.23528818786144257, 0.16251148283481598, 0.20514719188213348, 0.23327577114105225, 0.22864775359630585, 0.20791411399841309, 0.18507306277751923, 0.19645214080810547, 0.18542079627513885, 0.21295398473739624, 0.1534523218870163, 0.22318439185619354, 0.2692297101020813, 0.2221725732088089, 0.17383386194705963, 0.19964496791362762, 0.18310120701789856, 0.17352908849716187, 0.23669356107711792, 0.2220558077096939, 0.19586685299873352, 0.2849056124687195, 0.24348676204681396, 0.18383926153182983, 0.173893004655838, 0.21972709894180298, 0.1931130588054657, 0.20285850763320923, 0.19357654452323914, 0.25814682245254517, 0.23085036873817444, 0.20008979737758636, 0.22226126492023468, 0.21932296454906464, 0.19882957637310028, 0.17815764248371124, 0.2751637101173401, 0.22491370141506195, 0.2010001689195633, 0.23695960640907288, 0.21795348823070526, 0.20598769187927246, 0.19022700190544128, 0.16058719158172607, 0.24559971690177917, 0.20657847821712494, 0.27238163352012634, 0.14454925060272217, 0.2118762731552124, 0.30870485305786133, 0.1509855091571808, 0.27040502429008484, 0.22535373270511627, 0.15662837028503418, 0.20174074172973633, 0.19327060878276825, 0.1653720885515213, 0.1577749252319336, 0.2604633569717407, 0.194354847073555, 0.13776931166648865, 0.2206423580646515, 0.2536714971065521, 0.2052503228187561, 0.26670798659324646, 0.2767849266529083, 0.30206605792045593, 0.2260681539773941, 0.30530470609664917, 0.20491866767406464, 0.27065154910087585, 0.1856706142425537, 0.24675406515598297, 0.17615514993667603, 0.22946341335773468, 0.2638578414916992, 0.16657498478889465, 0.19035673141479492, 0.23215262591838837, 0.18303847312927246, 0.22916415333747864, 0.21035204827785492, 0.18608693778514862, 0.3109830617904663, 0.21576660871505737, 0.20745722949504852, 0.22090689837932587, 0.19606328010559082, 0.21845176815986633, 0.21903258562088013, 0.27762624621391296, 0.23508313298225403, 0.18536262214183807, 0.20314006507396698, 0.24044543504714966, 0.22538018226623535, 0.26733171939849854, 0.22046329081058502, 0.1975691169500351, 0.2201724350452423, 0.27540335059165955, 0.18944144248962402, 0.2622726261615753, 0.23506543040275574, 0.21917136013507843, 0.2325427234172821, 0.20441238582134247, 0.17382532358169556, 0.1469932645559311, 0.23935481905937195, 0.24654506146907806, 0.21041692793369293, 0.18666121363639832, 0.23323462903499603, 0.20912589132785797, 0.2127305120229721, 0.19871002435684204, 0.18265938758850098, 0.17535653710365295, 0.1899113804101944, 0.23549491167068481, 0.19273824989795685, 0.28419601917266846, 0.24389098584651947, 0.2399953007698059, 0.25243061780929565, 0.19436049461364746, 0.28288623690605164, 0.1883925050497055, 0.2092556208372116, 0.25211241841316223, 0.2514898180961609, 0.25355052947998047, 0.19497404992580414, 0.2762567102909088, 0.22655285894870758, 0.2224869430065155, 0.26039400696754456, 0.2728249132633209, 0.2511058449745178, 0.23670952022075653, 0.24235297739505768, 0.17723003029823303, 0.2430206686258316, 0.30894771218299866, 0.16160543262958527, 0.21283040940761566, 0.1682104468345642, 0.23410390317440033, 0.21009650826454163, 0.18996787071228027, 0.17705054581165314, 0.19355221092700958, 0.22266072034835815, 0.21473811566829681, 0.16719432175159454, 0.2019020915031433, 0.24316079914569855, 0.29499372839927673, 0.27364566922187805, 0.1854284256696701, 0.21317292749881744, 0.21839790046215057, 0.27691641449928284, 0.2551576495170593, 0.19938670098781586, 0.16941086947917938, 0.1836700737476349, 0.15417644381523132, 0.1554584503173828, 0.14122925698757172, 0.2759137749671936, 0.26224231719970703, 0.19026929140090942, 0.19581474363803864, 0.260140061378479, 0.24299676716327667, 0.20929878950119019, 0.26140421628952026, 0.2578074634075165, 0.22825564444065094, 0.26687386631965637, 0.1954348385334015, 0.20680774748325348, 0.22107923030853271, 0.25439202785491943, 0.1425858587026596, 0.21398036181926727, 0.21031570434570312, 0.207559272646904, 0.16781365871429443, 0.2099539190530777, 0.31657886505126953, 0.17747613787651062, 0.1856447011232376, 0.2157764434814453, 0.18334464728832245, 0.2143469899892807, 0.19531504809856415, 0.20564468204975128, 0.25072017312049866, 0.2687223553657532, 0.19339992105960846, 0.24550624191761017, 0.21260643005371094, 0.2172791212797165, 0.28275057673454285, 0.21231013536453247, 0.18174675107002258, 0.2711128294467926, 0.26918715238571167, 0.11627120524644852, 0.19477534294128418, 0.2429904341697693, 0.28077104687690735, 0.3125291168689728, 0.2551555335521698, 0.16900603473186493, 0.23954333364963531, 0.22858691215515137, 0.21105842292308807, 0.25729551911354065, 0.21999165415763855, 0.2441529482603073, 0.237619549036026, 0.22459155321121216, 0.22168482840061188, 0.17384913563728333, 0.29752928018569946, 0.23348374664783478, 0.23711594939231873, 0.20799358189105988, 0.22136130928993225, 0.25718924403190613, 0.1727173924446106, 0.22455726563930511, 0.21154125034809113, 0.251522034406662, 0.19461429119110107, 0.3025171160697937, 0.20942790806293488, 0.2613331079483032, 0.2593843340873718, 0.20338481664657593, 0.19237004220485687, 0.23244479298591614, 0.28224849700927734, 0.17867223918437958, 0.1769450306892395, 0.2442636787891388, 0.2515532970428467, 0.2016511708498001, 0.2015237808227539, 0.23153063654899597, 0.13403500616550446, 0.1967080980539322, 0.24085617065429688, 0.2343694269657135, 0.22219905257225037, 0.28255724906921387, 0.2531985342502594, 0.1814347356557846, 0.18860790133476257, 0.23987174034118652, 0.30046382546424866, 0.2033330798149109, 0.21915701031684875, 0.27533870935440063, 0.18614333868026733, 0.20653973519802094, 0.25435081124305725, 0.21654804050922394, 0.19176536798477173, 0.24211052060127258, 0.20528186857700348, 0.263935387134552, 0.18646281957626343, 0.22738035023212433, 0.2931457757949829, 0.2132292091846466, 0.17159853875637054, 0.17914696037769318, 0.16217650473117828, 0.21870630979537964, 0.23981164395809174, 0.20088322460651398, 0.2383631467819214, 2.6657042503356934, 2.618391752243042, 3.5841615200042725, 2.2070443630218506, 2.7341408729553223, 1.949892520904541, 2.7456953525543213, 2.774461030960083, 2.2435548305511475, 2.3681721687316895, 3.094621419906616, 2.1407129764556885, 2.908839702606201, 2.1513853073120117, 3.4090118408203125, 3.0402026176452637, 2.4131321907043457, 2.018397569656372, 1.6904776096343994, 2.4513211250305176, 1.973257064819336, 2.377868175506592, 2.5710220336914062, 2.9693515300750732, 3.1734941005706787, 2.1463780403137207, 1.736794352531433, 2.5764708518981934, 3.098827362060547, 1.75299072265625, 1.8669958114624023, 2.0985898971557617, 2.5289151668548584, 2.7338156700134277, 2.2055158615112305, 3.5389904975891113, 2.9523956775665283, 3.016552686691284, 1.4863518476486206, 2.15863037109375, 1.8394094705581665, 3.1208345890045166, 3.07659912109375, 2.0993080139160156, 2.6586108207702637, 2.313009262084961, 1.845911979675293, 2.26576828956604, 3.241542339324951, 2.863286018371582, 2.54498291015625, 3.3930728435516357, 3.2256054878234863, 3.6096408367156982, 2.5306150913238525, 1.5152828693389893, 2.277717351913452, 3.0094025135040283, 2.6219823360443115, 3.07828688621521, 3.8731529712677, 2.3977372646331787, 3.2586376667022705, 2.516960859298706, 3.374882936477661, 2.345167398452759, 1.6476125717163086, 1.357285737991333, 1.661049485206604, 1.8202139139175415, 2.137387752532959, 3.092449188232422, 2.2098641395568848, 2.9824047088623047, 2.2199325561523438, 2.3491549491882324, 2.0350968837738037, 1.9704220294952393, 1.8332780599594116, 3.6555633544921875, 3.4324216842651367, 1.815903902053833, 2.32759952545166, 3.745631694793701, 2.069514513015747, 3.1212356090545654, 2.756938934326172, 1.724570631980896, 2.670419931411743, 1.9380730390548706, 2.929669141769409, 1.6261191368103027, 2.5051069259643555, 1.589255928993225, 1.6801807880401611, 3.9856648445129395, 2.788421630859375, 1.8589859008789062, 2.5437381267547607, 2.411696672439575, 1.9038746356964111, 2.9064877033233643, 3.1643970012664795, 2.798445463180542, 2.02498459815979, 3.0029513835906982, 1.933971643447876, 2.1031675338745117, 3.351797103881836, 2.6741244792938232, 2.788518190383911, 3.3948380947113037, 2.4886903762817383, 2.123579740524292, 2.4343059062957764, 2.713120698928833, 2.0105957984924316, 2.166487693786621, 3.004490852355957, 3.7754135131835938, 2.3654098510742188, 2.373100757598877, 2.151097059249878, 1.9176899194717407, 3.242981433868408, 2.066882371902466, 1.9580892324447632, 1.932739496231079, 2.3854665756225586, 2.644521474838257, 2.7433464527130127, 3.5092289447784424, 3.0411198139190674, 3.2905831336975098, 1.5882034301757812, 2.08628511428833, 1.3287365436553955, 1.8471115827560425, 2.5742721557617188, 1.3235843181610107, 2.777639389038086, 3.2649102210998535, 2.4050958156585693, 2.336796283721924, 2.404371976852417, 1.789762258529663, 2.853119373321533, 1.6286201477050781, 1.5566421747207642, 3.0755302906036377, 1.7539091110229492, 3.482780933380127, 2.3629329204559326, 1.7278378009796143, 2.557408332824707, 1.765428066253662, 2.6706631183624268, 2.4608705043792725, 2.2833261489868164, 2.1007237434387207, 3.2627487182617188, 2.9084887504577637, 2.4792098999023438, 3.507321357727051, 2.4974539279937744, 2.956455707550049, 3.3670284748077393, 2.4900104999542236, 2.1906392574310303, 1.8648821115493774, 2.099252700805664, 1.9268842935562134, 1.9901490211486816, 2.366367816925049, 2.688981771469116, 2.4579291343688965, 2.6773457527160645, 1.9257802963256836, 4.463895797729492, 2.7747960090637207, 3.2478725910186768, 2.9574780464172363, 1.934529185295105, 2.4867000579833984, 2.3491158485412598, 1.8516374826431274, 2.6350107192993164, 2.5443243980407715, 1.6428457498550415, 1.9579757452011108, 1.9655424356460571, 2.158918619155884, 3.9560508728027344, 1.9013429880142212, 2.129220724105835, 1.6055196523666382, 1.8228302001953125, 1.7586376667022705, 2.430619716644287, 2.271444320678711, 1.4559298753738403, 2.3089795112609863, 2.6138975620269775, 2.5949296951293945, 2.5560715198516846, 3.2911975383758545, 1.8671495914459229, 2.575701951980591, 1.6912952661514282, 1.723433494567871, 1.5335057973861694, 2.2195825576782227, 2.237359046936035, 3.6764495372772217, 1.9050483703613281, 3.1861348152160645, 2.068331003189087, 3.8104467391967773, 1.8626540899276733, 2.5118751525878906, 2.747607946395874, 2.67852783203125, 1.4715244770050049, 3.588442802429199, 2.9707705974578857, 1.8476940393447876, 2.5936310291290283, 3.310413122177124, 1.4713451862335205, 3.0077691078186035, 2.2968199253082275, 2.6363449096679688, 3.365105152130127, 2.6524596214294434, 2.288266181945801, 2.943871021270752, 1.45159113407135, 2.6106250286102295, 1.7963881492614746, 2.4589810371398926, 2.806647539138794, 4.256422519683838, 1.9037100076675415, 2.20292329788208, 2.219337224960327, 2.0776638984680176, 1.915712594985962, 2.662848472595215, 2.6728146076202393, 2.205019474029541, 2.482931137084961, 2.7358715534210205, 2.3598527908325195, 3.1739120483398438, 3.213013172149658, 2.1607730388641357, 3.480933427810669, 2.3758959770202637, 2.2496533393859863, 2.328866481781006, 1.895630121231079, 2.011326313018799, 1.694252610206604, 1.720884919166565, 2.7114861011505127, 2.574298620223999, 2.8708412647247314, 2.562480926513672, 2.273813009262085, 1.3153457641601562, 3.0031254291534424, 1.8419551849365234, 2.570964813232422, 2.6791741847991943, 2.3235409259796143, 3.1759679317474365, 1.9290478229522705, 2.098351001739502, 2.1537680625915527, 2.2671279907226562, 1.7699053287506104, 1.9758682250976562, 2.1488606929779053, 3.334510087966919, 2.3539953231811523, 2.0514824390411377, 2.8735733032226562, 1.8943907022476196, 2.2556674480438232, 2.5831222534179688, 1.329256296157837, 1.3749210834503174, 2.2420473098754883, 3.1301681995391846, 1.8882111310958862, 1.5977951288223267, 2.9004406929016113, 2.7348852157592773, 2.6476991176605225, 2.868474245071411, 222.5303497314453, 355.89093017578125, 511.9412536621094, 166.00694274902344, 48.9605712890625, 307.2801208496094, 150.79884338378906, 227.51495361328125, 315.96893310546875, 41.934814453125, 99.45142364501953, 255.68017578125, 134.56622314453125, 90.07364654541016, 146.45654296875, 131.490966796875, 362.6516418457031, 53.3751220703125, 126.8621826171875, 62.623172760009766, 148.6832733154297, 134.80982971191406, 137.13201904296875, 49.38690185546875, 132.87501525878906, 123.92882537841797, 124.3188247680664, 229.69921875, 230.13885498046875, 145.6556396484375, 524.2616577148438, 201.72227478027344, 44.38650894165039, 240.97227478027344, 319.3717041015625, 362.6083068847656, 207.1209716796875, 79.80034637451172, 671.3611450195312, 71.70916748046875, 146.85101318359375, 58.77619171142578, 126.95494079589844, 182.68679809570312, 78.84579467773438, 211.06629943847656, 262.2611999511719, 220.9746856689453, 72.1904296875, 190.11683654785156, 177.67138671875, 183.7066192626953, 180.5088653564453, 61.276405334472656, 102.85672760009766, 60.54827880859375, 63.113162994384766, 71.380615234375, 141.4049530029297, 295.5622253417969, 49.456298828125, 123.67630767822266, 109.47071075439453, 68.29290771484375, 310.19525146484375, 196.33853149414062, 233.9873046875, 304.5458984375, 279.3307800292969, 97.9130859375, 47.722713470458984, 62.56906509399414, 100.25768280029297, 160.46739196777344, 175.98995971679688, 115.73109436035156, 91.9533462524414, 45.08277893066406, 253.3935089111328, 109.89697265625, 65.19365692138672, 300.8894958496094, 285.3688659667969, 183.67523193359375, 233.23919677734375, 116.96573638916016, 142.12408447265625, 225.4158935546875, 218.0956268310547, 46.86444091796875, 148.01959228515625, 149.44737243652344, 314.30755615234375, 110.77326202392578, 148.54620361328125, 36.06568145751953, 247.7744140625, 119.4627685546875, 106.09575653076172, 151.97567749023438, 349.86822509765625, 173.47299194335938, 173.398193359375, 228.78086853027344, 31.422508239746094, 130.6533966064453, 111.9271240234375, 128.98751831054688, 79.481201171875, 62.5191650390625, 73.51434326171875, 38.59649658203125, 161.00958251953125, 100.89921569824219, 78.7879638671875, 63.830379486083984, 91.58692932128906, 289.04547119140625, 201.07177734375, 171.75804138183594, 215.38499450683594, 46.093997955322266, 107.882080078125, 173.5519561767578, 78.80023193359375, 76.46977996826172, 179.35472106933594, 37.580745697021484, 36.015869140625, 105.26026916503906, 137.59622192382812, 126.04046630859375, 97.58263397216797, 130.0294952392578, 79.82928466796875, 258.9144287109375, 69.15009307861328, 250.8106231689453, 245.79510498046875, 128.22540283203125, 53.823387145996094, 190.9090576171875, 205.46612548828125, 260.0423583984375, 63.516414642333984, 592.3922729492188, 158.04312133789062, 215.3455047607422, 97.2505874633789, 108.43421936035156, 141.7005615234375, 224.33460998535156, 269.07696533203125, 53.66518783569336, 41.4898681640625, 403.0849609375, 150.47251892089844, 67.9881591796875, 59.44034957885742, 193.39122009277344, 138.1929473876953, 265.0105285644531, 654.922607421875, 82.2340087890625, 177.5573272705078, 358.27838134765625, 40.475341796875, 251.95921325683594, 109.13525390625, 312.15118408203125, 189.9658966064453, 281.47491455078125, 329.302734375, 50.12989044189453, 32.120697021484375, 71.44171905517578, 49.55517578125, 220.9643096923828, 239.849365234375, 96.53826141357422, 172.333740234375, 108.02208709716797, 379.5751953125, 64.27737426757812, 342.7879943847656, 95.99163818359375, 55.057918548583984, 92.68576049804688, 52.6754150390625, 360.0392761230469, 232.33792114257812, 146.87005615234375, 144.48004150390625, 203.10256958007812, 167.7113800048828, 212.44140625, 111.882568359375, 217.6669464111328, 64.4959716796875, 243.854248046875, 133.53045654296875, 413.11279296875, 58.42934799194336, 97.21758270263672, 97.47929382324219, 147.4704132080078, 32.735595703125, 150.169189453125, 157.31585693359375, 119.80712890625, 284.3583984375, 167.84521484375, 211.00341796875, 88.64393615722656, 255.4444122314453, 454.763427734375, 235.25880432128906, 177.5448760986328, 121.0265121459961, 175.907958984375, 345.95635986328125, 63.89225387573242, 166.08163452148438, 41.09613037109375, 216.41726684570312, 38.296142578125, 295.85162353515625, 215.53233337402344, 138.4189453125, 400.0060119628906, 283.1906433105469, 78.89991760253906, 153.124267578125, 178.91436767578125, 179.15953063964844, 62.73843002319336, 79.1429443359375, 277.428466796875, 132.2864990234375, 147.531494140625, 254.2997283935547, 364.830810546875, 298.9715881347656, 120.726806640625, 396.5174255371094, 308.6758117675781, 179.04913330078125, 185.54237365722656, 185.65652465820312, 221.93109130859375, 179.0009765625, 271.66357421875, 81.21431732177734, 355.96392822265625, 262.5426025390625, 53.98077392578125, 190.02569580078125, 34.84161376953125, 177.02622985839844, 115.65681457519531, 233.2431640625, 109.59468841552734, 72.67156982421875, 86.47802734375, 289.0011291503906, 136.04054260253906, 166.20394897460938, 166.0745849609375, 177.89077758789062, 432.4547424316406, 80.59868621826172, 93.56805419921875, 145.67559814453125, 381.21435546875, 405.9952392578125, 41.66717529296875, 63.60988235473633, 145.66168212890625, 167.48275756835938, 48.68680191040039, 331.31341552734375, 214.81585693359375, 177.63818359375, 111.2245101928711, 90.6351547241211, 359.33154296875, 211.7267303466797, 393.67919921875, 153.66854858398438, 180.1128692626953, 115.63124084472656, 74.449462890625, 175.0067138671875, 269.017578125, 192.26133728027344, 152.43858337402344, 211.1511993408203, 149.79092407226562, 138.0784912109375, 127.9145278930664, 3.882131338119507, 2.8083391189575195, 1.8341494798660278, 3.3865842819213867, 2.9347527027130127, 2.572141170501709, 3.6411662101745605, 2.7423300743103027, 1.804551601409912, 1.4551857709884644, 2.2572216987609863, 2.6108996868133545, 3.452136993408203, 3.2645580768585205, 2.470170259475708, 3.4682438373565674, 2.587299108505249, 3.709540605545044, 2.338454484939575, 1.966257095336914, 3.3624072074890137, 1.920145869255066, 2.2417404651641846, 2.8119847774505615, 2.72493314743042, 1.5034252405166626, 2.663609504699707, 2.0507726669311523, 3.0050783157348633, 3.934939384460449, 2.330203056335449, 1.9226000308990479, 2.573073625564575, 2.9454774856567383, 3.5327348709106445, 2.501795768737793, 2.1697607040405273, 2.4866249561309814, 2.7268896102905273, 1.794081687927246, 2.602458953857422, 2.3917226791381836, 2.9876677989959717, 3.373528480529785, 3.416093111038208, 2.476865530014038, 3.535922050476074, 1.9780962467193604, 1.68609619140625, 2.6625280380249023, 2.2528045177459717, 2.4378700256347656, 2.95306134223938, 3.351942300796509, 2.096980094909668, 1.785040259361267, 2.554584503173828, 1.6912544965744019, 3.018544912338257, 2.8902275562286377, 1.9834749698638916, 2.1890745162963867, 2.6529150009155273, 1.7657402753829956, 1.5138731002807617, 2.413640022277832, 2.7818334102630615, 2.558405876159668, 3.5346779823303223, 2.9237611293792725, 2.478992462158203, 3.026841402053833, 1.7884931564331055, 1.7900186777114868, 1.8867837190628052, 2.1865429878234863, 1.7478667497634888, 2.4440927505493164, 2.2287168502807617, 1.761297583580017, 2.9254817962646484, 1.9708547592163086, 3.242371082305908, 2.193140983581543, 2.9804370403289795, 3.4712462425231934, 3.9148058891296387, 2.043768882751465, 3.7978618144989014, 2.7299718856811523, 2.8992760181427, 2.8945627212524414, 3.729170560836792, 3.5652618408203125, 3.346325635910034, 1.735551357269287, 2.8992748260498047, 1.6347906589508057, 2.5778677463531494, 1.5429279804229736, 2.609200954437256, 3.412116289138794, 1.399636149406433, 3.128657579421997, 2.492102861404419, 3.3847644329071045, 3.6559553146362305, 3.1044909954071045, 3.3145220279693604, 3.911699056625366, 1.7934068441390991, 2.5840959548950195, 2.108447551727295, 2.671801805496216, 2.1529743671417236, 1.902024507522583, 3.380449056625366, 2.015507459640503, 2.6511614322662354, 2.5828258991241455, 2.8868870735168457, 2.6702663898468018, 3.3791897296905518, 1.7282570600509644, 2.8623898029327393, 1.7671340703964233, 1.3163518905639648, 2.2080113887786865, 3.2204670906066895, 1.300471305847168, 3.3421452045440674, 2.4586880207061768, 2.4944334030151367, 1.946547508239746, 3.1182267665863037, 2.217238187789917, 2.5887370109558105, 3.5884180068969727, 2.8064777851104736, 3.698214530944824, 2.198817253112793, 2.514521837234497, 1.6681063175201416, 2.3081674575805664, 1.9491872787475586, 3.826216459274292, 2.577770948410034, 2.059807777404785, 2.883345603942871, 3.8478851318359375, 2.0465691089630127, 2.632530450820923, 2.817967653274536, 3.4439268112182617, 3.2941465377807617, 3.4036357402801514, 3.298121213912964, 2.5537703037261963, 3.7700297832489014, 2.3117570877075195, 2.59635853767395, 2.300530433654785, 3.6982831954956055, 1.8636575937271118, 2.3030450344085693, 2.736132860183716, 2.1854541301727295, 1.9068878889083862, 3.3787951469421387, 3.195713996887207, 2.13791561126709, 2.574662446975708, 3.3130548000335693, 3.508500814437866, 3.548457145690918, 1.89708411693573, 3.1925582885742188, 3.190194606781006, 2.0179338455200195, 3.1387698650360107, 3.175884962081909, 2.254821538925171, 4.3822245597839355, 3.023557662963867, 3.8846218585968018, 1.5001575946807861, 1.247402310371399, 2.74916934967041, 3.952878952026367, 2.1824121475219727, 2.281553030014038, 2.570786714553833, 2.378697395324707, 2.609804630279541, 2.5870866775512695, 2.774729013442993, 2.2397451400756836, 2.330125331878662, 2.641005754470825, 2.913438081741333, 2.7159087657928467, 2.0264205932617188, 2.456864833831787, 2.868464946746826, 3.566739082336426, 3.5069940090179443, 2.9163143634796143, 1.867854118347168, 2.814044237136841, 2.366546392440796, 2.6098968982696533, 2.455796718597412, 2.45419979095459, 2.320056200027466, 2.986558198928833, 3.0548791885375977, 2.7674548625946045, 2.3258273601531982, 3.024796724319458, 2.9560582637786865, 2.1685171127319336, 3.0173027515411377, 2.948276996612549, 3.5244457721710205, 4.0980939865112305, 1.741136074066162, 3.4048376083374023, 2.2538061141967773, 2.171320915222168, 1.5428457260131836, 2.0412685871124268, 2.752671480178833, 2.059344530105591, 2.39437198638916, 3.18442440032959, 3.2708005905151367, 3.83964467048645, 2.4310784339904785, 3.462231397628784, 2.3498568534851074, 2.342237710952759, 3.6908035278320312, 3.100971221923828, 2.861952781677246, 1.513319969177246, 3.127335548400879, 2.4467270374298096, 4.2761759757995605, 3.012282133102417, 1.6745710372924805, 3.5249059200286865, 1.730592966079712, 1.9659881591796875, 3.219780206680298, 2.8887875080108643, 3.2414391040802, 2.281315803527832, 2.9285998344421387, 2.1600472927093506, 3.8900930881500244, 2.6367790699005127, 3.724538803100586, 1.2776505947113037, 2.5665910243988037, 2.612811326980591, 2.1410818099975586, 2.493962287902832, 2.7150659561157227, 2.9472453594207764, 2.478656053543091, 2.4843432903289795, 2.4356985092163086, 2.3340883255004883, 2.0477895736694336, 2.7557592391967773, 3.013572931289673, 1.8454750776290894, 2.3395986557006836, 2.6719391345977783, 2.309988021850586, 2.935145616531372, 1.744962453842163, 2.5107603073120117, 3.793044328689575, 4.043416500091553, 1.7984322309494019, 1.6721606254577637, 1.6508474349975586, 3.6119604110717773, 3.1073405742645264, 2.7158000469207764, 2.299981117248535, 3.7009856700897217, 2.6107378005981445, 3.6274735927581787, 2.2580347061157227, 2.096745491027832, 2.916926860809326, 2.029393196105957, 2.9245054721832275, 0.26692408323287964, 0.2506643533706665, 0.28211233019828796, 0.2245476245880127, 0.2640250027179718, 0.2551419734954834, 0.17106933891773224, 0.2026810646057129, 0.21419161558151245, 0.25660240650177, 0.23272563517093658, 0.24099071323871613, 0.2580724358558655, 0.23885641992092133, 0.2733857035636902, 0.2272355556488037, 0.22330959141254425, 0.20555800199508667, 0.26208746433258057, 0.25007903575897217, 0.2731020450592041, 0.20006099343299866, 0.24398724734783173, 0.21959197521209717, 0.21217940747737885, 0.18076728284358978, 0.19641967117786407, 0.19660015404224396, 0.21667346358299255, 0.1669943630695343, 0.2202547788619995, 0.24624991416931152, 0.2305128425359726, 0.2693324685096741, 0.23182924091815948, 0.2635369300842285, 0.1810312271118164, 0.21854491531848907, 0.2722119092941284, 0.2724169194698334, 0.2615760564804077, 0.3034447431564331, 0.16397148370742798, 0.24019916355609894, 0.30737045407295227, 0.22887206077575684, 0.1890953928232193, 0.22808527946472168, 0.279768168926239, 0.24575312435626984, 0.20898407697677612, 0.19753633439540863, 0.16625167429447174, 0.218319371342659, 0.1962946653366089, 0.24898679554462433, 0.2388824075460434, 0.16247153282165527, 0.2670630216598511, 0.30387163162231445, 0.24085590243339539, 0.22896277904510498, 0.26236817240715027, 0.19064128398895264, 0.19393950700759888, 0.23872168362140656, 0.1925722062587738, 0.21060077846050262, 0.2163723111152649, 0.19470305740833282, 0.2549411356449127, 0.18978889286518097, 0.18665337562561035, 0.17395715415477753, 0.30534422397613525, 0.18940216302871704, 0.21041524410247803, 0.2255484163761139, 0.2617889642715454, 0.17712374031543732, 0.27386611700057983, 0.23097433149814606, 0.24300025403499603, 0.24113218486309052, 0.17352676391601562, 0.21676161885261536, 0.24107463657855988, 0.2187139093875885, 0.2705782353878021, 0.22596068680286407, 0.19236136972904205, 0.26034465432167053, 0.2749415636062622, 0.21554799377918243, 0.1970434933900833, 0.30116143822669983, 0.19348466396331787, 0.22870080173015594, 0.17522335052490234, 0.24394643306732178, 0.28926560282707214, 0.2072392851114273, 0.18421919643878937, 0.24426543712615967, 0.2108570784330368, 0.21546564996242523, 0.18296024203300476, 0.1907574087381363, 0.2407756745815277, 0.32123249769210815, 0.23166993260383606, 0.2407664805650711, 0.23689423501491547, 0.2989196181297302, 0.22006206214427948, 0.1819184571504593, 0.23228120803833008, 0.21550460159778595, 0.262255996465683, 0.22654971480369568, 0.1872108280658722, 0.20262105762958527, 0.21329307556152344, 0.2093815952539444, 0.25838786363601685, 0.20300476253032684, 0.25852978229522705, 0.2590496838092804, 0.23608902096748352, 0.28741249442100525, 0.32722753286361694, 0.18541796505451202, 0.2798232138156891, 0.19773077964782715, 0.2339729219675064, 0.22992388904094696, 0.2906116545200348, 0.19614453613758087, 0.22848884761333466, 0.27484169602394104, 0.22664210200309753, 0.22541846334934235, 0.21998187899589539, 0.23649904131889343, 0.18526610732078552, 0.22674250602722168, 0.21449626982212067, 0.269325315952301, 0.21315863728523254, 0.2600216865539551, 0.2598961889743805, 0.21601884067058563, 0.24713654816150665, 0.24367205798625946, 0.23789195716381073, 0.14391158521175385, 0.20425502955913544, 0.17808154225349426, 0.2577723264694214, 0.15999211370944977, 0.21069194376468658, 0.21508418023586273, 0.23105745017528534, 0.2324002981185913, 0.16632938385009766, 0.2739664316177368, 0.19235679507255554, 0.3185727000236511, 0.21786737442016602, 0.1917746365070343, 0.26848286390304565, 0.2738044261932373, 0.20994821190834045, 0.22331000864505768, 0.29366132616996765, 0.22039401531219482, 0.20945216715335846, 0.23777084052562714, 0.20287446677684784, 0.20180274546146393, 0.14966480433940887, 0.21735484898090363, 0.27387621998786926, 0.23988474905490875, 0.21269908547401428, 0.20214858651161194, 0.2200423777103424, 0.20880953967571259, 0.1545034945011139, 0.21565616130828857, 0.2063627988100052, 0.21708530187606812, 0.18610413372516632, 0.20749828219413757, 0.1400669664144516, 0.2243325412273407, 0.22271192073822021, 0.24854305386543274, 0.22646771371364594, 0.25277137756347656, 0.20658667385578156, 0.25251322984695435, 0.25271305441856384, 0.19646766781806946, 0.17237257957458496, 0.229170560836792, 0.2143072485923767, 0.1650203913450241, 0.20876285433769226, 0.23450133204460144, 0.20776966214179993, 0.13419069349765778, 0.27697861194610596, 0.14721128344535828, 0.24111053347587585, 0.22355175018310547, 0.2416601926088333, 0.20134864747524261, 0.23868277668952942, 0.17042846977710724, 0.2188693881034851, 0.22046412527561188, 0.25070956349372864, 0.22168181836605072, 0.20700472593307495, 0.17104394733905792, 0.22728286683559418, 0.17857132852077484, 0.24172309041023254, 0.17102523148059845, 0.29789385199546814, 0.2485683709383011, 0.17503760755062103, 0.19506557285785675, 0.24167902767658234, 0.1563309133052826, 0.2250465750694275, 0.19196754693984985, 0.2008541375398636, 0.20682311058044434, 0.19969139993190765, 0.21540597081184387, 0.24920900166034698, 0.23935993015766144, 0.249334916472435, 0.2279280424118042, 0.15739049017429352, 0.23961709439754486, 0.19267867505550385, 0.18594543635845184, 0.21126878261566162, 0.2148466408252716, 0.20134727656841278, 0.2895543575286865, 0.15118905901908875, 0.16720540821552277, 0.22184120118618011, 0.23606085777282715, 0.250099778175354, 0.2785898447036743, 0.20389890670776367, 0.26487624645233154, 0.25307294726371765, 0.22320662438869476, 0.230742946267128, 0.22262731194496155, 0.23012052476406097, 0.21942555904388428, 0.24620111286640167, 0.2278863787651062, 0.25598207116127014, 0.24347341060638428, 0.20588931441307068, 0.2713243067264557, 0.28433337807655334, 0.23387065529823303, 0.21685096621513367, 0.22142812609672546, 0.22716598212718964, 0.2561815679073334, 0.1678837537765503, 0.27569663524627686, 0.2672407329082489, 0.27277979254722595, 0.28165203332901, 0.24569234251976013, 0.2697068452835083, 0.2810470759868622, 0.2248809039592743, 0.198167622089386, 0.2333291918039322, 0.16393132507801056, 0.2550542950630188, 0.14167693257331848, 0.2479165643453598, 0.25688400864601135, 0.2585345506668091, 0.23967596888542175, 0.17128203809261322, 0.21160674095153809, 2.631544351577759, 2.537356376647949, 2.2315523624420166, 2.4195308685302734, 1.8967869281768799, 2.276031494140625, 2.438349485397339, 3.397366762161255, 1.8279107809066772, 1.86199152469635, 1.585536003112793, 2.1474244594573975, 2.146545648574829, 1.7563199996948242, 2.2810468673706055, 1.9414507150650024, 2.09708571434021, 2.019979476928711, 2.0818397998809814, 1.9563134908676147, 1.9975484609603882, 2.264416217803955, 1.9797072410583496, 2.4237637519836426, 1.7540602684020996, 2.238922595977783, 2.4933509826660156, 2.643247604370117, 2.4172067642211914, 2.556716203689575, 2.1107449531555176, 2.2829525470733643, 2.6171910762786865, 1.9690978527069092, 2.60080885887146, 1.7388406991958618, 2.6780858039855957, 2.5533223152160645, 2.220595359802246, 3.211878538131714, 3.3129491806030273, 1.6974694728851318, 2.8611881732940674, 1.9577172994613647, 2.5793633460998535, 2.6176609992980957, 1.665132761001587, 2.417954444885254, 2.368816375732422, 3.913541078567505, 3.3489155769348145, 1.7231254577636719, 1.7432132959365845, 2.4523003101348877, 1.8630008697509766, 2.76938796043396, 1.8617947101593018, 1.4452654123306274, 2.3288519382476807, 2.5822389125823975, 2.653303861618042, 2.217808961868286, 2.9315478801727295, 2.0154380798339844, 1.4867089986801147, 3.4759325981140137, 2.541821002960205, 2.292447805404663, 2.7331066131591797, 1.888730764389038, 2.3782949447631836, 3.2434945106506348, 1.679726243019104, 2.062495470046997, 2.2862815856933594, 2.2875518798828125, 2.376201629638672, 2.8896734714508057, 3.2055561542510986, 1.9393268823623657, 2.864046573638916, 2.1091363430023193, 2.8646557331085205, 3.2354531288146973, 1.995286226272583, 2.5476596355438232, 2.565577983856201, 3.278676986694336, 2.8667430877685547, 1.6593296527862549, 1.8405579328536987, 1.744573950767517, 1.995508074760437, 2.018781900405884, 2.3329577445983887, 3.012516975402832, 2.449829339981079, 2.1879842281341553, 2.048577308654785, 1.5359989404678345, 1.7803951501846313, 2.948861837387085, 2.527625799179077, 3.1969311237335205, 2.480849504470825, 1.7605297565460205, 1.5509454011917114, 1.7359542846679688, 2.608938455581665, 2.7203240394592285, 1.2333050966262817, 3.268130302429199, 3.632413864135742, 1.8943325281143188, 2.4842844009399414, 2.6326708793640137, 1.837776780128479, 2.14957332611084, 2.25887393951416, 3.6693546772003174, 3.060438871383667, 2.400756359100342, 1.6664824485778809, 1.9563966989517212, 2.584754228591919, 2.6470558643341064, 2.304378032684326, 2.303280830383301, 3.441384792327881, 4.01436710357666, 3.0113918781280518, 2.907883882522583, 2.688169479370117, 1.9979408979415894, 2.0862343311309814, 1.754550576210022, 2.517653226852417, 2.2859702110290527, 2.16336727142334, 2.2635176181793213, 3.126704692840576, 2.1554811000823975, 2.780353307723999, 1.8192636966705322, 1.6113134622573853, 2.2206473350524902, 3.140090227127075, 4.159994602203369, 1.6243221759796143, 2.1539132595062256, 2.220160484313965, 2.9207675457000732, 3.776174545288086, 2.631307363510132, 2.10368013381958, 2.018582582473755, 2.409576416015625, 1.3766306638717651, 3.4670093059539795, 3.736117362976074, 2.5531909465789795, 1.8130918741226196, 1.4127857685089111, 1.7095190286636353, 3.269083261489868, 2.1094565391540527, 2.5670526027679443, 1.532562494277954, 2.0471444129943848, 3.1708080768585205, 2.9932861328125, 2.6889781951904297, 3.103483200073242, 1.9568108320236206, 2.114778995513916, 2.667771577835083, 2.0702250003814697, 2.6804327964782715, 2.7535645961761475, 1.9772999286651611, 2.6570591926574707, 2.1733827590942383, 3.4582653045654297, 1.623093843460083, 3.5326108932495117, 2.566746234893799, 3.025500535964966, 2.534285306930542, 1.8089803457260132, 1.7673135995864868, 1.7521194219589233, 3.2102863788604736, 1.616676926612854, 3.572479248046875, 2.3327548503875732, 1.525861144065857, 1.4339431524276733, 2.3759357929229736, 2.503117561340332, 2.329289436340332, 2.6576004028320312, 1.9968401193618774, 2.549849271774292, 2.701730489730835, 3.8140580654144287, 1.9262839555740356, 1.8569703102111816, 3.041980028152466, 3.53692626953125, 1.3411606550216675, 2.8640458583831787, 1.7147936820983887, 1.9685392379760742, 3.0788300037384033, 2.1746788024902344, 2.732785701751709, 2.0453219413757324, 1.2614285945892334, 2.866832733154297, 1.6081125736236572, 3.091298818588257, 1.9053308963775635, 1.7682756185531616, 2.9958653450012207, 2.670412540435791, 2.5574774742126465, 3.231560230255127, 2.1095364093780518, 3.270716428756714, 2.734652042388916, 2.630298376083374, 2.605192184448242, 2.8762757778167725, 2.0480082035064697, 2.8601810932159424, 1.7055416107177734, 3.215202808380127, 2.7339253425598145, 3.001955509185791, 2.7842488288879395, 2.431828498840332, 2.712144136428833, 2.995826005935669, 2.8381073474884033, 3.2170228958129883, 1.8001418113708496, 3.084308385848999, 1.3739728927612305, 2.7672417163848877, 1.1557782888412476, 2.3513755798339844, 2.2827095985412598, 2.6384692192077637, 2.746119737625122, 2.1626694202423096, 2.189765214920044, 1.727286696434021, 3.1503050327301025, 1.8980509042739868, 2.8496391773223877, 2.056098222732544, 2.4472007751464844, 2.522050619125366, 2.5796055793762207, 3.5296318531036377, 2.8014321327209473, 2.334398031234741, 2.9579567909240723, 1.580417275428772, 2.1228718757629395, 2.607107400894165, 2.411943197250366, 2.4006147384643555, 2.005378484725952, 3.3217544555664062, 2.222578763961792, 2.2209486961364746, 1.8469358682632446, 1.8750689029693604, 2.541224479675293, 3.161444902420044, 3.200305938720703, 2.244626045227051, 2.6757423877716064, 2.6698625087738037, 2.640324115753174, 3.1630043983459473, 2.026583433151245, 2.097137451171875, 1.4421970844268799, 1.9437615871429443, 2.639932155609131, 2.425130844116211, 3.340754985809326, 1.9542875289916992, 2.1339404582977295, 2.373521566390991, 4.641149997711182, 1.9499748945236206, 1.9909063577651978, 555.038818359375, 128.32005310058594, 140.268310546875, 126.74234008789062, 233.1634063720703, 359.7833557128906, 158.8011932373047, 44.529052734375, 111.96292877197266, 182.865234375, 118.03372955322266, 252.58363342285156, 224.287109375, 152.65545654296875, 80.05707550048828, 48.35546875, 226.010498046875, 112.772705078125, 326.98626708984375, 339.42352294921875, 117.40314483642578, 103.3446044921875, 31.034183502197266, 56.1171875, 217.12718200683594, 210.9037322998047, 64.25414276123047, 156.40086364746094, 109.74361419677734, 257.98455810546875, 180.5718536376953, 435.9914245605469, 81.14344024658203, 54.354496002197266, 196.79150390625, 387.1603698730469, 68.47346496582031, 455.4078674316406, 251.24627685546875, 175.5783233642578, 55.63763427734375, 283.7030944824219, 340.396240234375, 50.207489013671875, 111.82489776611328, 142.06900024414062, 230.6708984375, 145.6545867919922, 57.69935607910156, 168.76405334472656, 161.9105682373047, 67.21987915039062, 158.3099365234375, 129.9708709716797, 148.24615478515625, 65.2205810546875, 145.59527587890625, 219.70950317382812, 152.6503143310547, 77.40185546875, 180.628662109375, 193.24034118652344, 184.3311309814453, 188.4503936767578, 33.56048583984375, 142.91835021972656, 134.72142028808594, 127.69835662841797, 212.45281982421875, 213.140380859375, 162.73593139648438, 89.0198974609375, 559.6865234375, 261.5380859375, 202.9248046875, 198.259521484375, 255.3189239501953, 128.6059112548828, 623.1243896484375, 47.69053268432617, 354.8832092285156, 134.32861328125, 113.10956573486328, 140.72080993652344, 65.74951171875, 54.449607849121094, 111.48198699951172, 232.14373779296875, 272.4091796875, 58.103641510009766, 113.08427429199219, 73.55989837646484, 98.35467529296875, 152.25941467285156, 151.54229736328125, 47.71613693237305, 56.918182373046875, 104.96429443359375, 358.2908630371094, 719.279296875, 301.64837646484375, 202.7372283935547, 271.03289794921875, 158.81748962402344, 159.105712890625, 342.90435791015625, 152.46002197265625, 265.14349365234375, 219.6693878173828, 204.72384643554688, 96.62681579589844, 146.80531311035156, 364.4515686035156, 45.11115646362305, 319.150146484375, 52.355281829833984, 61.07177734375, 275.71240234375, 154.1569366455078, 134.67225646972656, 278.176513671875, 182.0535125732422, 120.54300689697266, 250.04666137695312, 140.93182373046875, 216.61192321777344, 180.08311462402344, 34.66492462158203, 420.4856872558594, 216.28143310546875, 188.2127685546875, 38.825706481933594, 237.868896484375, 247.9750518798828, 190.24777221679688, 505.0400390625, 73.933349609375, 231.47190856933594, 330.66510009765625, 201.59169006347656, 253.5292205810547, 279.61688232421875, 102.00471496582031, 276.44256591796875, 137.06112670898438, 189.87417602539062, 267.8231506347656, 331.2378845214844, 168.40234375, 57.01771926879883, 244.89273071289062, 63.81909942626953, 118.6078872680664, 484.4943542480469, 198.2529296875, 57.7431640625, 164.1160888671875, 222.35694885253906, 140.54617309570312, 121.89501953125, 241.881591796875, 89.50091552734375, 51.403202056884766, 107.55984497070312, 288.5555419921875, 67.96240234375, 83.65638732910156, 59.856204986572266, 120.23616027832031, 86.94091796875, 255.467529296875, 120.12599182128906, 296.0940246582031, 289.7647705078125, 189.1420440673828, 214.4558868408203, 115.24491882324219, 117.51567840576172, 508.8797302246094, 143.79867553710938, 38.69648742675781, 149.1544647216797, 83.34271240234375, 81.052978515625, 306.4566345214844, 97.8408203125, 87.65217590332031, 74.77020263671875, 118.22894287109375, 142.6718292236328, 214.38818359375, 196.6814422607422, 191.2761993408203, 246.847412109375, 299.2479248046875, 124.6189193725586, 184.0205078125, 120.89056396484375, 313.43096923828125, 257.671630859375, 112.4784927368164, 480.10015869140625, 359.23577880859375, 191.61874389648438, 135.62506103515625, 213.48204040527344, 113.01168060302734, 97.75341796875, 126.8111572265625, 43.79195785522461, 359.9161682128906, 374.08209228515625, 141.7255859375, 140.641357421875, 74.65204620361328, 351.24029541015625, 111.99837493896484, 333.7701416015625, 451.2886657714844, 56.032958984375, 131.29278564453125, 409.68890380859375, 237.3670196533203, 391.5218811035156, 288.94927978515625, 204.26007080078125, 183.6404571533203, 636.111328125, 102.15508270263672, 249.3269500732422, 65.41427612304688, 66.12830352783203, 62.9156494140625, 117.14901733398438, 207.42010498046875, 33.6431884765625, 103.04790496826172, 469.83135986328125, 246.69451904296875, 130.6484375, 393.3544006347656, 319.0693359375, 285.8553161621094, 71.19586181640625, 219.5943145751953, 228.76785278320312, 83.64336395263672, 396.1883850097656, 235.4617919921875, 143.4268341064453, 392.6614074707031, 248.2069854736328, 98.08672332763672, 257.06378173828125, 301.3885803222656, 73.58954620361328, 283.97222900390625, 421.085693359375, 89.5555191040039, 132.46498107910156, 181.939208984375, 201.68798828125, 43.44904708862305, 48.015380859375, 167.18812561035156, 220.5955810546875, 104.61997985839844, 221.661865234375, 98.9759750366211, 294.5129089355469, 270.0411376953125, 229.95361328125, 421.7303161621094, 78.48965454101562, 159.85023498535156, 236.49609375, 290.19403076171875, 78.47967529296875, 85.2518310546875, 89.6793212890625, 126.966796875, 33.99292755126953, 214.1658477783203, 187.3861083984375, 238.68507385253906, 481.0565490722656, 115.17623138427734, 199.57347106933594, 112.24327850341797, 205.37364196777344, 432.205078125, 483.365966796875, 97.1442642211914, 62.69134521484375, 305.1053466796875, 175.2996826171875, 255.3852081298828, 240.23793029785156, 82.99181365966797, 459.2921447753906, 2.8427670001983643, 2.730165719985962, 2.210198402404785, 1.524825096130371, 2.817594528198242, 2.0085947513580322, 2.4613282680511475, 3.5498173236846924, 2.775714159011841, 2.8867905139923096, 2.048764228820801, 3.140185594558716, 2.6361613273620605, 2.5491931438446045, 1.763619303703308, 3.562849760055542, 2.521733283996582, 1.3051730394363403, 2.7378530502319336, 2.261559009552002, 1.5211193561553955, 3.000969886779785, 3.155388355255127, 3.833627939224243, 2.1788361072540283, 2.6474010944366455, 3.262211799621582, 3.372004508972168, 3.0993754863739014, 2.9653332233428955, 3.1881182193756104, 3.1718850135803223, 1.5523338317871094, 3.3868157863616943, 2.4933176040649414, 3.8448846340179443, 2.2173140048980713, 2.2029149532318115, 3.485889196395874, 2.3438827991485596, 2.894667625427246, 2.6919212341308594, 2.417991876602173, 1.6969389915466309, 2.984257698059082, 1.534457802772522, 2.925867795944214, 2.228672504425049, 1.8035210371017456, 2.2937307357788086, 2.963364839553833, 2.7116405963897705, 3.671773910522461, 2.995807647705078, 3.52789306640625, 3.738356590270996, 3.2909951210021973, 1.141275405883789, 3.030949592590332, 1.65703284740448, 1.9078598022460938, 2.618870258331299, 2.6607866287231445, 3.146040678024292, 2.008479595184326, 1.8241852521896362, 3.6863622665405273, 1.9058208465576172, 2.2379791736602783, 2.0441160202026367, 1.4559011459350586, 2.856127977371216, 2.1235971450805664, 1.936518669128418, 3.373896598815918, 1.5162692070007324, 2.6443963050842285, 3.4057719707489014, 1.0709333419799805, 1.849076509475708, 1.5352813005447388, 2.1820147037506104, 3.4498918056488037, 1.4536221027374268, 2.683154344558716, 2.324195623397827, 2.6806206703186035, 2.2143778800964355, 3.015812873840332, 1.8516197204589844, 2.148409843444824, 1.958113670349121, 2.993924379348755, 3.119666337966919, 1.550881266593933, 4.382664680480957, 1.4855778217315674, 3.8355114459991455, 2.09287166595459, 3.581921339035034, 2.843693733215332, 1.961044430732727, 2.9387710094451904, 2.6671972274780273, 2.067753791809082, 1.4868948459625244, 2.5832273960113525, 2.4593124389648438, 2.042609214782715, 4.2480573654174805, 2.5036351680755615, 2.3510565757751465, 2.0697622299194336, 2.4494781494140625, 2.6780104637145996, 2.3791089057922363, 1.9803619384765625, 2.43591570854187, 3.2798736095428467, 3.346665620803833, 2.9342968463897705, 3.5669431686401367, 2.5399093627929688, 3.8647148609161377, 3.3376731872558594, 2.999730110168457, 2.7390007972717285, 1.7264913320541382, 2.2710118293762207, 2.4146335124969482, 2.5391786098480225, 3.2609777450561523, 3.7810583114624023, 3.1503875255584717, 3.046368360519409, 2.822880506515503, 1.6844391822814941, 3.3085222244262695, 1.7319669723510742, 2.423577070236206, 2.146167278289795, 1.600037693977356, 1.508828043937683, 2.245784044265747, 1.8846306800842285, 2.057656764984131, 3.9394140243530273, 3.006009340286255, 3.256002426147461, 3.095538377761841, 2.812575101852417, 3.105424165725708, 1.5372068881988525, 1.7698113918304443, 2.432530403137207, 1.8691473007202148, 1.9447983503341675, 2.2302064895629883, 1.4800596237182617, 2.986834764480591, 3.713313102722168, 2.9911835193634033, 2.479893684387207, 3.6552255153656006, 2.504915952682495, 3.4837939739227295, 4.226816177368164, 1.529579997062683, 2.407559394836426, 2.4881551265716553, 3.2964959144592285, 2.598268985748291, 1.715324878692627, 2.3917970657348633, 3.973978281021118, 2.2831661701202393, 2.993992805480957, 3.025883436203003, 2.2411246299743652, 2.1755971908569336, 2.0704843997955322, 2.665630340576172, 1.8930141925811768, 2.0836193561553955, 1.9691208600997925, 2.5973570346832275, 3.1614623069763184, 3.8743162155151367, 1.7303956747055054, 2.673832654953003, 3.1383259296417236, 3.378326416015625, 2.8864336013793945, 2.2396321296691895, 1.3063747882843018, 2.6153359413146973, 2.3265697956085205, 2.44171404838562, 2.8398759365081787, 2.403447151184082, 2.825263023376465, 2.955397367477417, 2.039475440979004, 3.15683650970459, 2.224909782409668, 1.9979963302612305, 2.180436849594116, 1.4642764329910278, 2.9300930500030518, 2.7939038276672363, 2.0669000148773193, 1.993183970451355, 2.727435350418091, 3.876335859298706, 2.8782622814178467, 2.9975228309631348, 2.445746421813965, 2.8319215774536133, 2.6280553340911865, 1.4668923616409302, 2.716214656829834, 2.13620662689209, 2.991978645324707, 3.485424757003784, 2.829869270324707, 3.2754783630371094, 2.700885057449341, 3.038031578063965, 1.5183477401733398, 2.7988977432250977, 2.8868210315704346, 2.777911424636841, 3.331390380859375, 2.186701774597168, 2.9098825454711914, 3.107165575027466, 3.1296932697296143, 3.4424993991851807, 1.524147868156433, 3.290764808654785, 2.6089813709259033, 2.912221670150757, 3.0158638954162598, 1.8894158601760864, 1.888589859008789, 3.6599035263061523, 2.909001588821411, 2.6890594959259033, 3.8074581623077393, 2.564563035964966, 2.5134835243225098, 1.801192283630371, 2.4810314178466797, 2.450307846069336, 2.8398845195770264, 3.0875158309936523, 3.420116424560547, 3.2119967937469482, 3.322904586791992, 2.1843461990356445, 2.9693825244903564, 2.4574661254882812, 4.378026008605957, 3.650517463684082, 2.2014355659484863, 2.544752836227417, 2.1651134490966797, 1.532002329826355, 1.946671962738037, 2.893979072570801, 3.6868772506713867, 1.4683489799499512, 2.855257272720337, 2.5401735305786133, 2.7798891067504883, 2.2735016345977783, 2.954838752746582, 3.312190532684326, 2.9026947021484375, 2.5516843795776367, 1.7589521408081055, 3.2122368812561035, 2.533601999282837, 2.6582024097442627, 3.1131176948547363, 1.9860302209854126, 2.462980270385742, 2.9349632263183594, 2.6024138927459717, 3.873417854309082, 2.767925977706909, 2.8998100757598877, 3.133294105529785, 3.6790971755981445, 2.5249931812286377, 2.595067024230957, 2.6512138843536377, 2.6015846729278564, 1.788735270500183, 3.1099464893341064, 0.2295251190662384, 0.16463690996170044, 0.23674851655960083, 0.20588469505310059, 0.22348931431770325, 0.2095501720905304, 0.23229646682739258, 0.20408190786838531, 0.23569747805595398, 0.20536355674266815, 0.22070938348770142, 0.2345258593559265, 0.23431897163391113, 0.22071906924247742, 0.20924785733222961, 0.20665879547595978, 0.15020295977592468, 0.2247675210237503, 0.2241932600736618, 0.16446135938167572, 0.2470749169588089, 0.24718549847602844, 0.21395055949687958, 0.187738299369812, 0.16799919307231903, 0.18570254743099213, 0.18708188831806183, 0.24914629757404327, 0.2887955904006958, 0.17710094153881073, 0.20191921293735504, 0.18526603281497955, 0.21727697551250458, 0.2221015840768814, 0.2609814405441284, 0.20121555030345917, 0.2145811766386032, 0.21604640781879425, 0.156550332903862, 0.18354545533657074, 0.2786160111427307, 0.2594507932662964, 0.21783214807510376, 0.2208378165960312, 0.224854975938797, 0.2507692873477936, 0.2862478494644165, 0.2793227434158325, 0.17606478929519653, 0.19237320125102997, 0.1898479014635086, 0.1989796757698059, 0.2061881572008133, 0.20738983154296875, 0.25082600116729736, 0.17105497419834137, 0.2137409895658493, 0.23317857086658478, 0.3275373876094818, 0.2171160876750946, 0.24456460773944855, 0.17126010358333588, 0.23497973382472992, 0.2571569085121155, 0.24983122944831848, 0.172657772898674, 0.30029281973838806, 0.16590616106987, 0.2263909876346588, 0.221079483628273, 0.19969812035560608, 0.1975560486316681, 0.26820486783981323, 0.2696244418621063, 0.2354126274585724, 0.27517855167388916, 0.1601046323776245, 0.17859525978565216, 0.25286319851875305, 0.21096265316009521, 0.2217503935098648, 0.22747230529785156, 0.26476866006851196, 0.19832836091518402, 0.16932067275047302, 0.23459647595882416, 0.22894781827926636, 0.2402421087026596, 0.22302594780921936, 0.26444414258003235, 0.24578841030597687, 0.20936797559261322, 0.1946277618408203, 0.20904238522052765, 0.18140578269958496, 0.23351699113845825, 0.14962607622146606, 0.2071126103401184, 0.1992352306842804, 0.2177034169435501, 0.2645922005176544, 0.2903997004032135, 0.16288742423057556, 0.2342333197593689, 0.192764550447464, 0.23115375638008118, 0.24221321940422058, 0.15337450802326202, 0.19235610961914062, 0.2629825174808502, 0.21024179458618164, 0.25169801712036133, 0.27845877408981323, 0.28276222944259644, 0.2709175944328308, 0.2156492918729782, 0.22890108823776245, 0.2254134714603424, 0.15558500587940216, 0.21733428537845612, 0.18980275094509125, 0.21384425461292267, 0.19690848886966705, 0.2386353760957718, 0.16836883127689362, 0.23709708452224731, 0.30240315198898315, 0.19549699127674103, 0.21300673484802246, 0.20952174067497253, 0.31482449173927307, 0.21518674492835999, 0.2723425030708313, 0.19006478786468506, 0.2921121418476105, 0.26788678765296936, 0.21130433678627014, 0.205585777759552, 0.2611015737056732, 0.23239226639270782, 0.23180055618286133, 0.21233879029750824, 0.17073272168636322, 0.191608265042305, 0.2350580096244812, 0.17413413524627686, 0.17733249068260193, 0.20815415680408478, 0.24515439569950104, 0.2224290817975998, 0.2514089047908783, 0.21231071650981903, 0.2898774743080139, 0.1605762392282486, 0.18686874210834503, 0.22702661156654358, 0.18906310200691223, 0.24111182987689972, 0.24732045829296112, 0.21306321024894714, 0.18300315737724304, 0.2799384295940399, 0.1926901936531067, 0.22458060085773468, 0.25915148854255676, 0.21077847480773926, 0.21656449139118195, 0.25911030173301697, 0.26450949907302856, 0.18487991392612457, 0.2160269320011139, 0.2291088104248047, 0.28661125898361206, 0.20045767724514008, 0.1832917034626007, 0.21243278682231903, 0.18521009385585785, 0.175771102309227, 0.2645561397075653, 0.2553243637084961, 0.2408062368631363, 0.1839883178472519, 0.23299308121204376, 0.29538848996162415, 0.16421771049499512, 0.2432599812746048, 0.17865313589572906, 0.2900124788284302, 0.1813504546880722, 0.15436124801635742, 0.1982780396938324, 0.23464663326740265, 0.26136988401412964, 0.21403834223747253, 0.1900472193956375, 0.1809292584657669, 0.2739959955215454, 0.1997922658920288, 0.18460260331630707, 0.2057158648967743, 0.17915134131908417, 0.1788305938243866, 0.18252645432949066, 0.1479894071817398, 0.21179264783859253, 0.28752169013023376, 0.2410833239555359, 0.2366601824760437, 0.1730763465166092, 0.26125627756118774, 0.157357320189476, 0.20748499035835266, 0.232713520526886, 0.1966625154018402, 0.19177992641925812, 0.2563336193561554, 0.2103530764579773, 0.1929360181093216, 0.2804216146469116, 0.2810436487197876, 0.19325487315654755, 0.24268363416194916, 0.23816637694835663, 0.2845621705055237, 0.17586922645568848, 0.26957032084465027, 0.19214259088039398, 0.21615904569625854, 0.24501466751098633, 0.22527103126049042, 0.19969329237937927, 0.23972289264202118, 0.20394565165042877, 0.1767171025276184, 0.1987878382205963, 0.21442584693431854, 0.19651198387145996, 0.18145155906677246, 0.2219296246767044, 0.2827812433242798, 0.19444942474365234, 0.20617595314979553, 0.23284302651882172, 0.27799904346466064, 0.27392563223838806, 0.25987473130226135, 0.23797981441020966, 0.24954280257225037, 0.22356043756008148, 0.17447593808174133, 0.32096099853515625, 0.23963485658168793, 0.22623790800571442, 0.1932421624660492, 0.1842670440673828, 0.20510722696781158, 0.23016341030597687, 0.20958520472049713, 0.2683789134025574, 0.2202358990907669, 0.2326970398426056, 0.21899443864822388, 0.2460574358701706, 0.2863253355026245, 0.23273277282714844, 0.23990511894226074, 0.28536516427993774, 0.23336921632289886, 0.2225356101989746, 0.26279857754707336, 0.2281866818666458, 0.17872267961502075, 0.20008383691310883, 0.22562026977539062, 0.17726461589336395, 0.2818211019039154, 0.17474691569805145, 0.17489182949066162, 0.24745944142341614, 0.18105605244636536, 0.19902610778808594, 0.2216828167438507, 0.2380090206861496, 0.22536994516849518, 0.19081607460975647, 0.1779358983039856, 0.17444045841693878, 0.22108684480190277, 0.20020611584186554, 0.2166597694158554, 0.2579983174800873, 0.22136324644088745, 0.23085112869739532, 0.20563581585884094, 0.3033846914768219, 0.2221049964427948, 0.283910870552063, 0.2411862164735794, 0.22273138165473938, 0.23646663129329681, 3.245455741882324, 4.546928405761719, 3.3205478191375732, 1.5430757999420166, 2.743837833404541, 2.388190269470215, 2.5597081184387207, 2.483536958694458, 2.10037899017334, 3.1629440784454346, 2.284085750579834, 2.436406135559082, 2.1972532272338867, 3.254554033279419, 1.621720790863037, 2.461548328399658, 2.3503613471984863, 2.0351133346557617, 3.2473442554473877, 2.8312318325042725, 2.3630809783935547, 2.9552059173583984, 2.7249209880828857, 2.2160913944244385, 3.5272743701934814, 2.7068657875061035, 1.7975597381591797, 2.9804744720458984, 2.4004886150360107, 3.000591278076172, 1.372920036315918, 3.102931261062622, 1.576946496963501, 2.819899320602417, 3.9074342250823975, 2.101684331893921, 2.323018789291382, 2.2004196643829346, 2.6164441108703613, 3.654937744140625, 2.1149144172668457, 1.8749662637710571, 2.942223072052002, 2.6428887844085693, 3.1893882751464844, 2.3216073513031006, 2.512101888656616, 2.041616678237915, 3.054941415786743, 2.7083306312561035, 3.5141868591308594, 2.737927198410034, 2.9103951454162598, 2.0900208950042725, 3.420482635498047, 1.8772531747817993, 2.48427152633667, 1.7979272603988647, 1.957457184791565, 2.672339677810669, 2.3617918491363525, 2.7841885089874268, 2.9812381267547607, 2.5725905895233154, 3.150958299636841, 2.264800786972046, 3.108402729034424, 2.52189040184021, 2.079174280166626, 2.428499460220337, 3.5302319526672363, 2.8157711029052734, 2.5322422981262207, 3.26434063911438, 2.8738133907318115, 2.6824607849121094, 3.5482890605926514, 2.450767993927002, 2.4656829833984375, 3.4913079738616943, 2.5688769817352295, 2.1505227088928223, 3.006619691848755, 3.404188871383667, 2.678936004638672, 1.8742120265960693, 1.8259872198104858, 2.1505391597747803, 1.328774094581604, 2.568556547164917, 1.5336328744888306, 2.1797094345092773, 2.464143991470337, 2.7060089111328125, 1.6903594732284546, 2.255986213684082, 3.044968843460083, 2.343221664428711, 2.297499418258667, 1.8462189435958862, 2.231572389602661, 3.2277913093566895, 1.624636173248291, 1.7943856716156006, 2.046196937561035, 1.6496118307113647, 2.4659252166748047, 2.3444509506225586, 2.5168521404266357, 2.186117172241211, 2.9045867919921875, 2.602984666824341, 1.7413467168807983, 1.7092170715332031, 3.2304766178131104, 2.8696389198303223, 2.8618993759155273, 1.7867240905761719, 2.6085896492004395, 2.078447103500366, 2.9858508110046387, 2.381380319595337, 2.1104860305786133, 2.7079412937164307, 2.12477445602417, 2.65545916557312, 3.759387731552124, 2.2919936180114746, 2.431704044342041, 2.416612386703491, 1.3283277750015259, 1.9110009670257568, 2.559185028076172, 1.8107125759124756, 1.8399196863174438, 2.4480066299438477, 2.4253833293914795, 2.9509098529815674, 2.303931474685669, 1.8852802515029907, 2.891369581222534, 2.7021307945251465, 2.1227855682373047, 1.5653116703033447, 2.27231502532959, 1.8540302515029907, 1.9769548177719116, 2.945146322250366, 2.0287046432495117, 1.9371830224990845, 3.0554521083831787, 2.270714044570923, 1.8898833990097046, 2.9995598793029785, 3.171637773513794, 2.1060831546783447, 2.945507764816284, 2.122617244720459, 1.7844780683517456, 3.5979089736938477, 2.1021649837493896, 2.2014920711517334, 2.994016647338867, 3.2018959522247314, 3.224320888519287, 1.9768829345703125, 3.1391193866729736, 2.572072744369507, 2.3163270950317383, 2.502033233642578, 2.1143903732299805, 2.582961320877075, 1.7171446084976196, 2.4400057792663574, 2.4674370288848877, 3.1402134895324707, 2.351609945297241, 2.7097408771514893, 1.7851248979568481, 3.1357579231262207, 2.712070941925049, 2.0527584552764893, 3.1795730590820312, 1.359571099281311, 4.077774524688721, 2.9790279865264893, 2.6755638122558594, 2.5361857414245605, 2.937103271484375, 3.448824882507324, 3.203947067260742, 2.54044508934021, 1.9370452165603638, 2.8285961151123047, 2.9717113971710205, 2.5189754962921143, 2.0804262161254883, 3.4204888343811035, 2.6293530464172363, 2.0674657821655273, 2.415847063064575, 3.2764575481414795, 2.9033093452453613, 3.011075973510742, 2.5677592754364014, 2.2727339267730713, 2.0639777183532715, 2.8096134662628174, 2.6852822303771973, 2.2893600463867188, 3.0253007411956787, 2.7938268184661865, 1.8291536569595337, 2.0316362380981445, 3.174384355545044, 3.9599990844726562, 2.598102331161499, 2.3078787326812744, 2.661738157272339, 2.721698045730591, 2.1041553020477295, 1.806679368019104, 3.3933632373809814, 2.893714189529419, 3.356945037841797, 4.081955909729004, 2.082150936126709, 2.200335741043091, 2.410019874572754, 2.064675807952881, 3.6515579223632812, 2.467604398727417, 3.2505931854248047, 2.714707612991333, 2.2978646755218506, 2.2550036907196045, 1.683782935142517, 2.811108350753784, 2.6571459770202637, 2.0980725288391113, 2.6559219360351562, 2.946258544921875, 3.099313259124756, 3.251298189163208, 2.5376358032226562, 1.9282041788101196, 2.7629470825195312, 2.418813467025757, 2.3951644897460938, 2.4896275997161865, 2.7265625, 2.6049792766571045, 3.309920072555542, 2.0406384468078613, 1.77764892578125, 2.395322799682617, 2.808337450027466, 2.0098493099212646, 1.965967059135437, 3.0736522674560547, 2.6210644245147705, 1.7158807516098022, 3.7605679035186768, 2.0270872116088867, 4.047765731811523, 2.900402784347534, 2.6939873695373535, 3.0251660346984863, 2.4858133792877197, 2.213715076446533, 1.86297607421875, 1.9667720794677734, 2.395275115966797, 1.894059419631958, 1.4129388332366943, 2.1195068359375, 2.931018590927124, 2.306447744369507, 1.7723177671432495, 2.3643481731414795, 2.844177722930908, 1.6263996362686157, 2.4183664321899414, 3.4526584148406982, 2.0150046348571777, 1.5993419885635376, 2.562596321105957, 3.4494597911834717, 1.8754665851593018, 3.3481273651123047, 3.3607869148254395, 1.4876409769058228, 1.9910738468170166, 2.1461193561553955, 1.9620399475097656, 2.966383695602417, 2.6684811115264893, 1.8346765041351318, 3.915841817855835, 2.1863348484039307, 121.59523010253906, 167.03558349609375, 398.8321838378906, 121.33110809326172, 213.98988342285156, 242.10902404785156, 66.70925903320312, 88.6373062133789, 177.7150421142578, 188.61167907714844, 258.7386779785156, 278.9068603515625, 349.40264892578125, 225.7021484375, 246.88931274414062, 71.517822265625, 150.03497314453125, 192.87451171875, 416.3059997558594, 203.6111297607422, 107.77628326416016, 389.0362854003906, 61.470619201660156, 54.19501876831055, 613.4501953125, 158.98663330078125, 403.8224182128906, 284.1576232910156, 185.7645263671875, 194.2831573486328, 211.22854614257812, 188.5448455810547, 247.37124633789062, 252.43760681152344, 150.11587524414062, 150.4044647216797, 324.5692443847656, 318.4112548828125, 92.69268035888672, 43.03997802734375, 118.80284881591797, 161.11407470703125, 168.98585510253906, 235.8485107421875, 180.8231201171875, 90.30347442626953, 450.0377197265625, 215.55242919921875, 306.54010009765625, 430.12017822265625, 330.6249084472656, 177.2977752685547, 103.7996826171875, 115.4991683959961, 133.19921875, 272.7100830078125, 130.40980529785156, 177.61546325683594, 109.55979919433594, 57.15296173095703, 45.14215850830078, 86.52651977539062, 165.75140380859375, 136.13999938964844, 405.9950256347656, 198.3979034423828, 411.96588134765625, 71.12345886230469, 145.448974609375, 181.2250518798828, 75.36580657958984, 441.6983947753906, 220.80316162109375, 184.0027313232422, 180.5313262939453, 99.46125030517578, 316.80902099609375, 127.38599395751953, 206.61184692382812, 97.79736328125, 174.17605590820312, 67.5709228515625, 138.7900390625, 219.2215576171875, 111.2523193359375, 125.1930923461914, 118.11817932128906, 231.30967712402344, 139.224853515625, 64.5389404296875, 387.8410339355469, 93.10804748535156, 214.6707763671875, 264.92034912109375, 369.5066833496094, 361.4189758300781, 131.00274658203125, 79.23140716552734, 91.33349609375, 224.2510528564453, 117.53759765625, 309.8802185058594, 307.4056701660156, 522.2939453125, 373.0209045410156, 88.7623062133789, 69.18860626220703, 122.87950897216797, 169.14385986328125, 483.7291259765625, 86.3988037109375, 304.22369384765625, 113.14800262451172, 119.42630767822266, 161.09329223632812, 108.78173828125, 262.16656494140625, 112.66680145263672, 214.42469787597656, 297.59405517578125, 111.63893127441406, 649.1071166992188, 134.87933349609375, 42.42813491821289, 330.6763916015625, 270.71307373046875, 215.14442443847656, 345.1175842285156, 57.424129486083984, 148.6054229736328, 111.55606079101562, 255.2459259033203, 289.67547607421875, 123.372314453125, 127.77066802978516, 187.08950805664062, 42.930721282958984, 52.7723388671875, 180.0233917236328, 169.1581268310547, 221.7943878173828, 241.08030700683594, 257.18609619140625, 242.60487365722656, 104.58194732666016, 261.5040283203125, 246.1439971923828, 180.92112731933594, 198.4031524658203, 108.04376983642578, 378.4698791503906, 107.3656005859375, 145.11968994140625, 254.7147216796875, 46.34503936767578, 230.12860107421875, 84.35784912109375, 190.18408203125, 217.7185821533203, 74.3582763671875, 105.728515625, 274.1188659667969, 91.8448257446289, 316.5917053222656, 99.62873077392578, 402.3099060058594, 96.30765533447266, 274.3671875, 363.3995666503906, 334.9236755371094, 99.34124755859375, 169.5705108642578, 54.4586181640625, 225.051513671875, 347.0785217285156, 195.5467987060547, 274.19586181640625, 122.90626525878906, 268.8378601074219, 495.4281005859375, 283.3167724609375, 71.5634536743164, 314.3128662109375, 41.6737060546875, 124.84814453125, 113.17261505126953, 94.3173828125, 170.2537078857422, 280.31280517578125, 118.96099090576172, 40.5306396484375, 230.73399353027344, 246.8330841064453, 183.2486114501953, 94.60125732421875, 230.73741149902344, 268.6318359375, 84.69525146484375, 312.6133117675781, 120.77031707763672, 45.23681640625, 171.62600708007812, 330.7452697753906, 74.0017318725586, 234.3513946533203, 95.814208984375, 285.71258544921875, 54.865291595458984, 37.12738800048828, 245.5606231689453, 273.038818359375, 204.8150177001953, 100.51702880859375, 288.9374694824219, 187.6634521484375, 206.80050659179688, 80.13380432128906, 84.75067138671875, 98.95136260986328, 311.1854553222656, 183.82347106933594, 244.9897003173828, 68.84844970703125, 145.2421875, 136.63665771484375, 351.6661682128906, 84.36134338378906, 365.69482421875, 182.08421325683594, 341.43023681640625, 65.400146484375, 67.75806427001953, 228.6520233154297, 113.16650390625, 285.5818176269531, 115.3973388671875, 194.06654357910156, 123.89930725097656, 104.69696044921875, 305.59326171875, 137.80645751953125, 45.708309173583984, 93.24478149414062, 188.4012908935547, 318.5998840332031, 87.57984924316406, 58.095741271972656, 72.39222717285156, 104.3520278930664, 44.59677505493164, 90.671630859375, 180.4949188232422, 200.98265075683594, 75.89177703857422, 124.95197296142578, 191.20985412597656, 131.82530212402344, 233.1631317138672, 147.66990661621094, 75.99069213867188, 448.330078125, 356.9185791015625, 281.5950927734375, 263.52642822265625, 77.27825927734375, 86.57331848144531, 239.4082794189453, 59.5810546875, 166.36587524414062, 193.6660919189453, 178.35023498535156, 182.2039337158203, 117.31829833984375, 121.74982452392578, 405.7326354980469, 245.97622680664062, 105.3206787109375, 196.56410217285156, 108.91646575927734, 195.59573364257812, 306.0555419921875, 425.1103515625, 109.78997802734375, 155.13311767578125, 135.62960815429688, 254.49432373046875, 176.34288024902344, 210.802490234375, 116.18976593017578, 235.42718505859375, 137.7486114501953, 174.68370056152344, 170.92837524414062, 174.80433654785156, 149.2127685546875, 116.141357421875, 287.655029296875, 209.6905975341797, 152.7222442626953, 346.2445373535156, 1.6968576908111572, 2.9274511337280273, 2.641841173171997, 2.6813268661499023, 1.4131137132644653, 2.985491991043091, 3.235751152038574, 3.07993745803833, 2.3815219402313232, 2.360952138900757, 4.015588283538818, 3.1002166271209717, 3.7237675189971924, 2.788588285446167, 2.6890976428985596, 2.9552221298217773, 2.679131507873535, 1.7768545150756836, 2.487971544265747, 2.91864013671875, 3.269047737121582, 1.220604658126831, 2.4974265098571777, 2.587186336517334, 3.4507839679718018, 1.9953869581222534, 3.4842729568481445, 2.8844029903411865, 1.0629634857177734, 2.2310540676116943, 1.7736343145370483, 2.93222713470459, 2.8849730491638184, 2.5829057693481445, 3.1404449939727783, 2.7133781909942627, 3.8586301803588867, 3.37591290473938, 2.56973934173584, 3.10201358795166, 2.4608023166656494, 1.567042350769043, 3.4809751510620117, 2.082575798034668, 3.974332094192505, 3.8011767864227295, 2.6138386726379395, 3.687108039855957, 3.0160675048828125, 2.950030565261841, 2.6900243759155273, 2.2323966026306152, 2.632868528366089, 2.253046751022339, 2.20578670501709, 3.8621575832366943, 3.6157543659210205, 1.8061083555221558, 2.104611396789551, 2.904494524002075, 2.5499696731567383, 2.4062206745147705, 2.1668460369110107, 2.328251838684082, 2.121933937072754, 3.113672971725464, 1.969541311264038, 3.770104169845581, 2.3008697032928467, 3.1661996841430664, 3.1721062660217285, 1.9292949438095093, 2.3699769973754883, 3.0646069049835205, 2.0959177017211914, 3.241938591003418, 3.3871548175811768, 2.9290783405303955, 4.16744327545166, 2.191577672958374, 2.649249315261841, 2.0637876987457275, 2.7242443561553955, 2.567824125289917, 2.957073926925659, 2.837825298309326, 3.488987922668457, 1.8541277647018433, 2.07108211517334, 1.1751166582107544, 1.8853940963745117, 3.8757755756378174, 3.733088970184326, 3.2004778385162354, 1.7895445823669434, 3.2576382160186768, 1.3406802415847778, 2.657794237136841, 2.4558234214782715, 3.5339508056640625, 1.8905013799667358, 3.191218137741089, 3.58090877532959, 2.630457639694214, 2.4369759559631348, 3.7305843830108643, 4.030886173248291, 2.673035144805908, 2.5149779319763184, 2.231055498123169, 1.4630364179611206, 3.5743207931518555, 3.5800886154174805, 2.8911828994750977, 2.170102119445801, 1.9662798643112183, 2.981041193008423, 1.4575376510620117, 2.225815773010254, 1.823238492012024, 2.456681489944458, 3.508570432662964, 2.944951057434082, 2.9476406574249268, 2.3325247764587402, 2.6139416694641113, 3.3369176387786865, 1.8664488792419434, 2.6499955654144287, 2.2148451805114746, 2.1897501945495605, 1.6235359907150269, 2.1562814712524414, 2.525456428527832, 3.0066635608673096, 3.3337488174438477, 2.3488664627075195, 3.2433712482452393, 3.363544225692749, 3.403648853302002, 2.269005060195923, 2.783588171005249, 2.012478828430176, 2.6923065185546875, 1.8972524404525757, 1.2607773542404175, 2.586014986038208, 2.346371650695801, 3.013713836669922, 2.9359734058380127, 2.3013365268707275, 2.4527978897094727, 2.6383159160614014, 2.398430824279785, 2.2771964073181152, 2.85275936126709, 3.0211575031280518, 2.887071371078491, 2.6084868907928467, 2.613872528076172, 3.836757183074951, 2.7782833576202393, 3.4065093994140625, 3.7561633586883545, 2.2640221118927, 4.232253074645996, 2.571948289871216, 2.2822582721710205, 3.331033945083618, 2.5403759479522705, 2.8514087200164795, 3.809194326400757, 1.5657700300216675, 3.1106157302856445, 2.487720012664795, 3.2527873516082764, 2.420485734939575, 2.33620548248291, 1.7584905624389648, 3.8289635181427, 2.2724435329437256, 2.5654897689819336, 3.284867525100708, 1.8578176498413086, 2.8772192001342773, 4.074897766113281, 3.07812237739563, 1.4347469806671143, 1.6196775436401367, 2.828568696975708, 2.7710137367248535, 2.746608018875122, 2.3143727779388428, 3.630439281463623, 3.8205349445343018, 3.136152982711792, 3.001861810684204, 1.7512545585632324, 4.1581926345825195, 2.2261955738067627, 3.837038516998291, 1.6109404563903809, 1.7497014999389648, 2.544492244720459, 2.04154109954834, 1.5510456562042236, 2.5036098957061768, 2.5865635871887207, 2.964247941970825, 3.088574171066284, 2.6937973499298096, 2.35588002204895, 3.126269578933716, 1.941048502922058, 2.949479341506958, 3.3394439220428467, 3.1474218368530273, 2.5673282146453857, 2.50692081451416, 2.5438356399536133, 2.332280158996582, 2.819805145263672, 2.7084033489227295, 1.9766360521316528, 2.568554639816284, 2.4672365188598633, 3.137455463409424, 2.9773552417755127, 2.4987781047821045, 1.9315528869628906, 1.4557818174362183, 1.8557968139648438, 2.909710645675659, 3.6287028789520264, 3.499375581741333, 2.104011297225952, 1.5938787460327148, 2.8537988662719727, 2.3646535873413086, 2.5477752685546875, 3.9899609088897705, 1.9873589277267456, 3.38759183883667, 2.729506254196167, 1.8279467821121216, 2.7515692710876465, 3.911389112472534, 2.509951591491699, 2.7562530040740967, 1.1289187669754028, 3.013611316680908, 2.740413188934326, 1.7576452493667603, 2.8143627643585205, 2.1372976303100586, 2.2752950191497803, 2.4667656421661377, 2.8670871257781982, 3.206822395324707, 2.4943418502807617, 2.6493029594421387, 2.533994197845459, 2.8649840354919434, 2.2543725967407227, 3.155318260192871, 3.2779617309570312, 3.490756034851074, 2.07791805267334, 2.5108842849731445, 3.067967414855957, 1.576075553894043, 2.788342237472534, 3.5262866020202637, 2.131596565246582, 2.6965320110321045, 2.1195003986358643, 2.957728862762451, 3.656284809112549, 1.9983892440795898, 1.855507731437683, 3.195194721221924, 2.3701906204223633, 1.6725213527679443, 2.035975694656372, 3.3920505046844482, 2.7210497856140137, 1.4245405197143555, 2.947648286819458, 1.9474111795425415, 3.970172643661499, 3.1579692363739014, 2.4509706497192383, 4.457643508911133, 2.9549529552459717, 3.303148031234741, 2.3977839946746826, 3.772988796234131, 3.802371025085449, 3.1673924922943115, 2.4548254013061523, 0.2570731043815613, 0.27443283796310425, 0.22210663557052612, 0.23227080702781677, 0.16319942474365234, 0.20523768663406372, 0.18088237941265106, 0.17685432732105255, 0.18624663352966309, 0.2522590160369873, 0.2734740674495697, 0.25656622648239136, 0.2294437140226364, 0.22912566363811493, 0.13078558444976807, 0.20357190072536469, 0.19150114059448242, 0.23729334771633148, 0.21508647501468658, 0.21759149432182312, 0.2847267985343933, 0.2177002727985382, 0.2642029821872711, 0.29527193307876587, 0.21145470440387726, 0.26634255051612854, 0.2609117031097412, 0.25015372037887573, 0.19376540184020996, 0.2667274475097656, 0.21612225472927094, 0.26441559195518494, 0.2534235417842865, 0.1996086835861206, 0.28773233294487, 0.23071344196796417, 0.1628815233707428, 0.20677341520786285, 0.23896117508411407, 0.283253937959671, 0.2489379495382309, 0.2417093813419342, 0.19793164730072021, 0.1935337334871292, 0.23064792156219482, 0.19063468277454376, 0.25377097725868225, 0.1951245814561844, 0.19568519294261932, 0.30567631125450134, 0.25781500339508057, 0.15697312355041504, 0.23438647389411926, 0.22674234211444855, 0.1851760894060135, 0.17527015507221222, 0.22036097943782806, 0.2253614217042923, 0.2265167236328125, 0.2107027918100357, 0.2174156904220581, 0.18040937185287476, 0.2808389663696289, 0.19088114798069, 0.23354464769363403, 0.17277975380420685, 0.2514148950576782, 0.22979409992694855, 0.22556403279304504, 0.27164971828460693, 0.15428172051906586, 0.20796653628349304, 0.28553837537765503, 0.20374955236911774, 0.2813086211681366, 0.2513095438480377, 0.18672116100788116, 0.16804514825344086, 0.18418972194194794, 0.2413250356912613, 0.23583249747753143, 0.20340247452259064, 0.18222682178020477, 0.16228096187114716, 0.24490800499916077, 0.21948719024658203, 0.209080770611763, 0.24198226630687714, 0.21580921113491058, 0.17902244627475739, 0.21582873165607452, 0.14681623876094818, 0.18619592487812042, 0.2402563840150833, 0.2633257508277893, 0.2871972322463989, 0.21775905787944794, 0.22264079749584198, 0.24577505886554718, 0.22423142194747925, 0.2404642254114151, 0.27656233310699463, 0.2214967906475067, 0.2738133370876312, 0.22091445326805115, 0.2575168311595917, 0.2175469696521759, 0.22363686561584473, 0.22133269906044006, 0.20728778839111328, 0.2638006806373596, 0.1961420327425003, 0.2181987762451172, 0.179341122508049, 0.21008777618408203, 0.20724818110466003, 0.19668525457382202, 0.2949657440185547, 0.21333955228328705, 0.2582699656486511, 0.2273457646369934, 0.25417277216911316, 0.20058883726596832, 0.24210670590400696, 0.19271411001682281, 0.27530747652053833, 0.2201799601316452, 0.22734586894512177, 0.2506141662597656, 0.3131293058395386, 0.21484500169754028, 0.3188774883747101, 0.21036973595619202, 0.2433640956878662, 0.29400530457496643, 0.23584231734275818, 0.18485482037067413, 0.2207280695438385, 0.17233416438102722, 0.16203689575195312, 0.26849162578582764, 0.2031530886888504, 0.24020735919475555, 0.14861126244068146, 0.22698821127414703, 0.22488662600517273, 0.21725113689899445, 0.29554665088653564, 0.1754007637500763, 0.20487670600414276, 0.2863539457321167, 0.28545597195625305, 0.2320823222398758, 0.22595851123332977, 0.23242045938968658, 0.1872602254152298, 0.19372659921646118, 0.19917094707489014, 0.15456731617450714, 0.2600838541984558, 0.24380813539028168, 0.2589764893054962, 0.19224466383457184, 0.23097780346870422, 0.21423858404159546, 0.20786738395690918, 0.23774491250514984, 0.13401645421981812, 0.1608734130859375, 0.24771440029144287, 0.2378520518541336, 0.2744733691215515, 0.23804020881652832, 0.2301119565963745, 0.28163889050483704, 0.22506116330623627, 0.32286587357521057, 0.20535427331924438, 0.2664317190647125, 0.2321307361125946, 0.20025640726089478, 0.2552413046360016, 0.22595471143722534, 0.21380554139614105, 0.20527689158916473, 0.22578543424606323, 0.20285606384277344, 0.17014169692993164, 0.23650749027729034, 0.23657019436359406, 0.26332831382751465, 0.20996184647083282, 0.24448339641094208, 0.19209568202495575, 0.26927584409713745, 0.2667561173439026, 0.25884291529655457, 0.2046133428812027, 0.2189660370349884, 0.24111436307430267, 0.2263033092021942, 0.22313135862350464, 0.20924794673919678, 0.28096315264701843, 0.3008330166339874, 0.18158793449401855, 0.22663018107414246, 0.2844144403934479, 0.25769373774528503, 0.2629280686378479, 0.24984772503376007, 0.21440047025680542, 0.18633435666561127, 0.13027173280715942, 0.13906824588775635, 0.22602245211601257, 0.21011272072792053, 0.24177595973014832, 0.21739055216312408, 0.18283286690711975, 0.16576947271823883, 0.18099841475486755, 0.2136402130126953, 0.16742175817489624, 0.2534242570400238, 0.2192268669605255, 0.2914848327636719, 0.18532665073871613, 0.3118131160736084, 0.20119285583496094, 0.20899972319602966, 0.24930191040039062, 0.26419201493263245, 0.23967547714710236, 0.20863741636276245, 0.15502744913101196, 0.18959276378154755, 0.19775401055812836, 0.2665533423423767, 0.20339921116828918, 0.16855943202972412, 0.1812586486339569, 0.2184034138917923, 0.19312071800231934, 0.20189960300922394, 0.20698247849941254, 0.18312378227710724, 0.27041804790496826, 0.3073466122150421, 0.21838180720806122, 0.2816956639289856, 0.22567908465862274, 0.2051224708557129, 0.23325379192829132, 0.17776742577552795, 0.20501261949539185, 0.20996716618537903, 0.17046256363391876, 0.2966902554035187, 0.19150201976299286, 0.23568592965602875, 0.17060506343841553, 0.2059411257505417, 0.25322744250297546, 0.22865235805511475, 0.2239028513431549, 0.22485387325286865, 0.18971358239650726, 0.24938972294330597, 0.22190974652767181, 0.2536683678627014, 0.19887423515319824, 0.3053132891654968, 0.2174157053232193, 0.19981952011585236, 0.25259166955947876, 0.21400263905525208, 0.2572237253189087, 0.25860387086868286, 0.22414159774780273, 0.24045509099960327, 0.1830393373966217, 0.21178431808948517, 0.2621757984161377, 0.21324102580547333, 0.22126218676567078, 0.18157267570495605, 0.2698530852794647, 0.15800288319587708, 0.25892066955566406, 0.22575487196445465, 0.23738570511341095, 0.2510400712490082, 0.2983449399471283, 0.21128615736961365, 0.24783171713352203, 0.18832935392856598, 0.26626142859458923, 0.16165925562381744, 0.2200450450181961, 2.4428906440734863, 2.2783043384552, 1.6146066188812256, 2.5453624725341797, 2.6557953357696533, 2.549513578414917, 3.2229373455047607, 3.593182325363159, 1.9719034433364868, 3.6266980171203613, 3.213456392288208, 3.2288105487823486, 3.0683491230010986, 1.4929193258285522, 3.0441341400146484, 2.0776710510253906, 3.3096377849578857, 1.8881193399429321, 1.8797857761383057, 2.259753465652466, 2.928603410720825, 2.317300319671631, 2.2991294860839844, 1.7959835529327393, 3.0488951206207275, 2.570115804672241, 2.311021327972412, 2.1416258811950684, 3.105975389480591, 2.500627279281616, 2.209735631942749, 2.7186989784240723, 2.1101889610290527, 2.849813461303711, 3.034625291824341, 2.032524585723877, 2.1772756576538086, 2.724026679992676, 2.4219255447387695, 2.2318971157073975, 1.7989534139633179, 1.8965438604354858, 2.337785243988037, 2.173159122467041, 2.4603562355041504, 3.8811235427856445, 3.5465168952941895, 2.5040664672851562, 2.8952717781066895, 2.1029107570648193, 2.621368885040283, 2.8953769207000732, 2.8788774013519287, 2.907762289047241, 1.9922960996627808, 1.399442434310913, 2.2556686401367188, 1.7636809349060059, 2.6542346477508545, 2.8110320568084717, 1.7457348108291626, 1.9322302341461182, 2.1998305320739746, 1.812839150428772, 4.1066389083862305, 2.694650411605835, 2.3203344345092773, 2.411911964416504, 2.1659321784973145, 3.0895538330078125, 2.718026876449585, 4.181906223297119, 4.033953666687012, 2.381286859512329, 3.011059522628784, 2.5860278606414795, 2.7626659870147705, 3.0742383003234863, 2.305894136428833, 2.9130265712738037, 2.5106773376464844, 2.515439987182617, 3.3400344848632812, 2.190294027328491, 3.6085386276245117, 2.5508875846862793, 2.1860463619232178, 2.0853984355926514, 2.0007638931274414, 2.60304856300354, 2.3954074382781982, 2.653656482696533, 3.3060123920440674, 1.6730146408081055, 3.5823421478271484, 3.016862154006958, 2.513302803039551, 2.353923797607422, 2.105630397796631, 2.9221718311309814, 2.668963670730591, 2.0744340419769287, 3.6156725883483887, 3.089879035949707, 2.549034595489502, 2.5718159675598145, 2.2830090522766113, 3.0670058727264404, 2.8607165813446045, 3.183446168899536, 4.059091567993164, 2.8248355388641357, 1.928383469581604, 2.1700356006622314, 3.702641725540161, 2.33184814453125, 3.1263585090637207, 3.3733127117156982, 2.160539388656616, 1.4705145359039307, 3.991640567779541, 3.8615663051605225, 3.8769664764404297, 1.4206316471099854, 1.7846421003341675, 1.9147840738296509, 2.1267189979553223, 2.456979990005493, 2.948305606842041, 2.8148224353790283, 2.3679728507995605, 2.0962679386138916, 1.5289891958236694, 2.3850412368774414, 3.2219364643096924, 3.579331636428833, 1.7569212913513184, 2.6765429973602295, 2.4702072143554688, 2.5788650512695312, 1.9979686737060547, 2.6308977603912354, 2.224444627761841, 4.619357585906982, 2.8368260860443115, 2.7477898597717285, 3.447024345397949, 2.074632406234741, 2.1085002422332764, 1.5751049518585205, 2.3279757499694824, 2.2243902683258057, 2.364131450653076, 3.651625394821167, 1.7827093601226807, 2.3878533840179443, 3.0720036029815674, 3.2017393112182617, 2.824815034866333, 2.0212788581848145, 2.7394161224365234, 2.6947262287139893, 2.930314302444458, 2.8907580375671387, 2.0483691692352295, 2.6601784229278564, 2.4884936809539795, 2.0642967224121094, 3.0487587451934814, 1.335432767868042, 1.7495237588882446, 2.340712308883667, 2.081437826156616, 2.675553560256958, 2.20939564704895, 3.550910234451294, 2.5722758769989014, 1.8204113245010376, 2.580883026123047, 2.061821460723877, 2.0556492805480957, 2.057880401611328, 3.6696853637695312, 3.2938473224639893, 2.968532085418701, 1.99573814868927, 2.5990350246429443, 1.9050207138061523, 3.355663776397705, 1.947622299194336, 1.7018226385116577, 2.300788640975952, 2.8909366130828857, 3.616203784942627, 2.106797218322754, 3.1916110515594482, 2.2897896766662598, 2.1458587646484375, 1.9913784265518188, 1.8339296579360962, 3.532865524291992, 2.6696693897247314, 1.4865883588790894, 3.256373882293701, 2.4065299034118652, 1.9840443134307861, 2.0126748085021973, 2.258430242538452, 3.437624454498291, 1.746909499168396, 2.731320858001709, 2.480203866958618, 2.9841079711914062, 2.0345253944396973, 3.0650439262390137, 3.779996871948242, 2.855438709259033, 2.59012508392334, 1.2311158180236816, 1.9090999364852905, 3.5630345344543457, 2.1299421787261963, 3.9375686645507812, 2.487075090408325, 2.5869805812835693, 2.03255295753479, 2.283430814743042, 2.8390185832977295, 2.0047764778137207, 2.458936929702759, 2.2048230171203613, 2.374811887741089, 1.9122557640075684, 2.1577248573303223, 2.3390603065490723, 2.30104660987854, 2.044743537902832, 3.4810991287231445, 1.8260947465896606, 3.650902271270752, 2.575773239135742, 2.099724769592285, 2.812065601348877, 2.585453510284424, 3.393162488937378, 2.9199764728546143, 2.3226680755615234, 1.7206732034683228, 1.7869142293930054, 2.5288524627685547, 2.675360918045044, 1.6229872703552246, 2.188912868499756, 2.2133803367614746, 3.090918779373169, 2.525869369506836, 2.127854824066162, 1.6016302108764648, 1.7935301065444946, 1.6613638401031494, 3.8166515827178955, 2.2250478267669678, 2.668797254562378, 3.48382568359375, 2.8634796142578125, 2.691559314727783, 2.209696054458618, 2.0620312690734863, 2.276686668395996, 2.145799160003662, 2.786445140838623, 2.524993419647217, 2.3464343547821045, 1.4710890054702759, 2.5357980728149414, 2.8593227863311768, 2.474043130874634, 2.6901931762695312, 2.640613317489624, 2.0691921710968018, 3.937307357788086, 3.551478862762451, 1.644304633140564, 2.0799672603607178, 2.209353446960449, 3.3219215869903564, 2.2074687480926514, 3.271259069442749, 2.1155922412872314, 2.5819365978240967, 2.2935991287231445, 2.671462297439575, 1.6446037292480469, 2.1963701248168945, 2.847062349319458, 3.173915386199951, 3.292759418487549, 2.617422103881836, 2.0907278060913086, 2.3225631713867188, 180.35569763183594, 161.86756896972656, 295.13043212890625, 252.03265380859375, 108.2591552734375, 86.21914672851562, 239.3834686279297, 114.89318084716797, 94.76417541503906, 222.8963165283203, 427.1708984375, 86.25556182861328, 301.4168701171875, 373.8575744628906, 96.82582092285156, 342.3628845214844, 191.83624267578125, 60.85791015625, 156.76576232910156, 250.874755859375, 490.5078125, 74.1258544921875, 71.333984375, 432.4152526855469, 149.619384765625, 49.100711822509766, 146.27865600585938, 107.23114013671875, 288.2738342285156, 254.1053009033203, 387.0843811035156, 263.15576171875, 250.2880859375, 299.3923645019531, 211.7842559814453, 110.42745208740234, 248.3304443359375, 163.38951110839844, 94.50999450683594, 471.19561767578125, 253.0106201171875, 160.8612518310547, 243.00547790527344, 222.3025360107422, 438.8971252441406, 38.05975341796875, 209.8548126220703, 150.4647216796875, 149.57379150390625, 165.38330078125, 239.41741943359375, 153.38204956054688, 91.07440185546875, 40.98602294921875, 182.07086181640625, 235.21641540527344, 132.11474609375, 122.90650177001953, 318.55401611328125, 51.61834716796875, 117.23384857177734, 56.716278076171875, 76.75067138671875, 197.22769165039062, 259.0974426269531, 273.1962585449219, 37.645751953125, 298.797607421875, 138.36610412597656, 159.650634765625, 142.93045043945312, 149.26690673828125, 228.17738342285156, 137.8162384033203, 124.22521209716797, 366.95562744140625, 153.8794708251953, 135.04241943359375, 50.920745849609375, 245.40106201171875, 39.28662109375, 97.8831787109375, 154.53155517578125, 108.26607513427734, 68.24649047851562, 59.907470703125, 38.77789306640625, 186.83457946777344, 234.1727294921875, 49.364070892333984, 443.5179443359375, 207.0054473876953, 158.3905792236328, 59.12458419799805, 188.8763427734375, 167.1071014404297, 103.30936431884766, 120.29994201660156, 398.7750549316406, 196.5340576171875, 143.9528045654297, 159.69403076171875, 111.64360809326172, 213.5906524658203, 285.6496276855469, 244.96209716796875, 145.50637817382812, 99.46412658691406, 98.33768463134766, 209.11273193359375, 170.47874450683594, 58.15241241455078, 425.451171875, 144.14984130859375, 156.15882873535156, 100.98712921142578, 347.7967224121094, 201.3980255126953, 50.17120361328125, 46.699520111083984, 105.00188446044922, 131.4207763671875, 152.07791137695312, 162.324462890625, 298.1770324707031, 403.3246765136719, 43.880615234375, 149.1238250732422, 147.43682861328125, 446.0777893066406, 163.93276977539062, 365.85687255859375, 104.28369140625, 170.8539276123047, 130.39125061035156, 71.76239776611328, 210.66864013671875, 45.56797409057617, 339.0565185546875, 77.56380462646484, 256.4620666503906, 103.78533935546875, 286.47119140625, 207.001708984375, 76.97412109375, 453.6622619628906, 49.24436569213867, 55.7159423828125, 108.46527099609375, 147.53456115722656, 464.1376953125, 406.168701171875, 341.62841796875, 180.55381774902344, 213.6527862548828, 195.28810119628906, 58.95274353027344, 98.1241226196289, 217.29217529296875, 217.1666717529297, 119.074462890625, 418.4855041503906, 298.38922119140625, 92.68402099609375, 184.4872283935547, 324.3468017578125, 282.18017578125, 102.95765686035156, 148.76702880859375, 49.94760513305664, 319.8445739746094, 139.63861083984375, 322.8322448730469, 152.081298828125, 90.93877410888672, 77.98439025878906, 244.9585723876953, 143.479248046875, 73.45922088623047, 195.6273193359375, 112.4285888671875, 245.5985565185547, 73.61841583251953, 245.2459716796875, 84.10160064697266, 244.2154998779297, 120.5731201171875, 179.8787384033203, 35.8533935546875, 218.87750244140625, 145.04067993164062, 111.892578125, 182.9041748046875, 309.0802917480469, 138.71258544921875, 154.84124755859375, 266.5950012207031, 128.2069854736328, 91.83224487304688, 73.4435806274414, 339.5380859375, 518.5947265625, 69.59375, 120.51177215576172, 261.4013366699219, 196.55528259277344, 185.6609649658203, 285.91326904296875, 148.94200134277344, 113.63652801513672, 113.72720336914062, 290.7343444824219, 244.90771484375, 197.1717529296875, 314.0362854003906, 172.10960388183594, 194.7166290283203, 64.0985107421875, 430.050537109375, 138.6123809814453, 93.84066009521484, 57.60198211669922, 124.78401947021484, 152.92051696777344, 243.0564727783203, 213.27003479003906, 241.923828125, 248.5043487548828, 90.43875885009766, 186.16624450683594, 80.66358947753906, 48.42333984375, 167.54620361328125, 72.887939453125, 96.32743072509766, 96.67523193359375, 365.8528747558594, 98.273193359375, 241.6084747314453, 206.75827026367188, 71.0862045288086, 423.5910949707031, 73.14886474609375, 215.35464477539062, 200.25547790527344, 171.23452758789062, 385.92779541015625, 206.80377197265625, 133.82937622070312, 130.929931640625, 260.4580383300781, 207.7686309814453, 68.02166748046875, 174.59483337402344, 74.12374114990234, 297.84326171875, 255.75994873046875, 257.0693054199219, 267.2804870605469, 73.00306701660156, 378.83740234375, 147.1000213623047, 57.251277923583984, 197.0326385498047, 51.155643463134766, 298.807373046875, 104.93782043457031, 163.5736083984375, 151.88919067382812, 198.0077362060547, 431.395263671875, 63.8580322265625, 219.8118896484375, 71.7694091796875, 62.31189727783203, 163.92999267578125, 92.07112884521484, 248.119384765625, 48.19493103027344, 166.49468994140625, 159.42713928222656, 49.89072036743164, 85.14585876464844, 69.81230926513672, 179.284912109375, 163.63836669921875, 80.075927734375, 286.2740478515625, 158.64854431152344, 279.0565490722656, 170.81455993652344, 111.2005615234375, 128.72982788085938, 143.987548828125, 227.9922637939453, 177.8188018798828, 51.9093017578125, 113.60118865966797, 131.9412841796875, 66.6495361328125, 3.36065411567688, 3.477187395095825, 4.0663275718688965, 1.6749529838562012, 2.830004930496216, 1.9090594053268433, 3.0803215503692627, 2.150672674179077, 2.683732271194458, 4.241869926452637, 3.2852728366851807, 2.3788747787475586, 2.669603109359741, 3.34744930267334, 2.750495195388794, 1.5489660501480103, 1.4931038618087769, 2.434645891189575, 2.1330108642578125, 2.790510892868042, 2.6143290996551514, 2.6609630584716797, 3.5990781784057617, 2.215402364730835, 2.7812700271606445, 1.469929575920105, 1.8902068138122559, 2.1966257095336914, 2.3223369121551514, 3.4873626232147217, 2.3392317295074463, 2.0035245418548584, 3.447070837020874, 2.047185182571411, 2.096156597137451, 1.8041393756866455, 2.9307470321655273, 2.3634493350982666, 2.8657586574554443, 2.7996840476989746, 3.137838125228882, 1.4757736921310425, 2.0932226181030273, 2.858590841293335, 2.67813777923584, 2.8293774127960205, 2.7822086811065674, 1.7864625453948975, 3.384333610534668, 2.911951780319214, 2.8479156494140625, 3.4956274032592773, 2.8542613983154297, 1.7470251321792603, 2.149245023727417, 2.454829454421997, 3.0738747119903564, 2.772935152053833, 2.451934337615967, 3.0421159267425537, 1.9551900625228882, 3.286756753921509, 2.680755615234375, 3.641474485397339, 2.2315590381622314, 3.4662792682647705, 2.8838114738464355, 1.8472442626953125, 3.7643535137176514, 3.559516191482544, 3.533726692199707, 2.5464792251586914, 3.6114892959594727, 2.0874643325805664, 2.207871437072754, 2.7491486072540283, 3.030181884765625, 2.4370529651641846, 1.1906319856643677, 2.955949068069458, 2.364068031311035, 2.6909584999084473, 3.5962016582489014, 3.0412745475769043, 2.9808154106140137, 2.9678544998168945, 2.2618095874786377, 2.832512855529785, 3.4268553256988525, 2.246232032775879, 1.9944632053375244, 2.2141237258911133, 1.8450287580490112, 3.22100567817688, 3.493424654006958, 3.459805727005005, 2.505072593688965, 2.6591293811798096, 1.7225093841552734, 2.2593088150024414, 2.960120677947998, 3.251162528991699, 2.7286882400512695, 3.211367130279541, 3.014496326446533, 1.6762856245040894, 2.6459267139434814, 1.5658477544784546, 3.017008066177368, 3.501683235168457, 1.9830259084701538, 2.3991432189941406, 1.6142040491104126, 3.5550413131713867, 1.9852077960968018, 2.644101619720459, 2.8342676162719727, 1.5356322526931763, 1.6560240983963013, 2.766249418258667, 3.0653655529022217, 1.2567540407180786, 1.8117362260818481, 2.8532490730285645, 2.2480132579803467, 2.7170610427856445, 3.041433334350586, 3.6589598655700684, 1.7527964115142822, 2.692296028137207, 1.80559241771698, 1.8004311323165894, 3.091418504714966, 2.947343587875366, 2.9722096920013428, 3.0913407802581787, 2.2199087142944336, 2.463885545730591, 2.4580602645874023, 3.405641794204712, 2.7617897987365723, 1.9496831893920898, 3.404618501663208, 2.3372302055358887, 2.0692548751831055, 3.105494260787964, 1.6971099376678467, 2.2743844985961914, 4.049460411071777, 3.732131242752075, 2.304161310195923, 2.7088212966918945, 4.467541217803955, 2.5587644577026367, 2.8008508682250977, 1.7219877243041992, 2.1315832138061523, 2.409653663635254, 1.9824801683425903, 1.4189502000808716, 3.1488115787506104, 3.058311939239502, 1.8854925632476807, 1.6930761337280273, 3.2186801433563232, 3.0494494438171387, 2.527785062789917, 2.940234422683716, 2.6766083240509033, 3.6269826889038086, 2.1206307411193848, 1.9334553480148315, 2.462010383605957, 2.51967191696167, 3.2765989303588867, 2.2646236419677734, 1.4559868574142456, 3.46757435798645, 2.431859016418457, 2.6661272048950195, 3.7744381427764893, 3.2847793102264404, 3.6572048664093018, 2.316094398498535, 1.6405380964279175, 3.6683971881866455, 2.5927515029907227, 2.181553840637207, 2.7140069007873535, 2.64810848236084, 1.8296319246292114, 2.5844154357910156, 2.2232866287231445, 2.97563099861145, 3.6912355422973633, 2.7016453742980957, 3.7980833053588867, 2.7821807861328125, 2.217003345489502, 4.057962417602539, 3.1733920574188232, 2.3666696548461914, 2.870701789855957, 1.9530096054077148, 2.6998376846313477, 3.5609045028686523, 2.1504225730895996, 2.6337993144989014, 3.6072421073913574, 2.1547415256500244, 2.7932634353637695, 2.8668909072875977, 3.5645318031311035, 2.5635790824890137, 1.7823147773742676, 3.0801329612731934, 2.4736545085906982, 2.998399019241333, 2.804934024810791, 1.9147224426269531, 2.5850048065185547, 3.7757792472839355, 3.2966549396514893, 1.0424115657806396, 2.457211971282959, 3.5293071269989014, 2.72039794921875, 3.0277535915374756, 1.6981171369552612, 1.3987590074539185, 3.0921738147735596, 1.509670376777649, 3.552067756652832, 3.7562360763549805, 2.8527328968048096, 3.4321019649505615, 3.7590792179107666, 3.311202049255371, 2.4491052627563477, 3.32259464263916, 1.4381121397018433, 2.26747989654541, 2.613523006439209, 1.2265539169311523, 3.63917875289917, 2.9304168224334717, 2.6033220291137695, 4.317072868347168, 2.2887675762176514, 2.469194173812866, 2.744642496109009, 2.079087257385254, 2.731116771697998, 3.0561635494232178, 2.604231595993042, 1.840483546257019, 2.182100772857666, 2.84896183013916, 1.1568918228149414, 2.7453701496124268, 1.758843183517456, 3.5863451957702637, 1.7277822494506836, 2.183108329772949, 3.2924132347106934, 2.9663915634155273, 2.3696467876434326, 2.0441370010375977, 2.5904152393341064, 2.10732364654541, 1.8417366743087769, 2.329461097717285, 2.1875619888305664, 2.160890579223633, 3.279572010040283, 2.224492073059082, 2.600922107696533, 3.9275753498077393, 3.451930046081543, 2.614924192428589, 3.1059277057647705, 3.0756731033325195, 1.675510048866272, 1.7911819219589233, 1.848565936088562, 2.478875160217285, 2.1732797622680664, 2.1497609615325928, 2.3266992568969727, 3.088810920715332, 2.1598832607269287, 3.3300929069519043, 2.0829434394836426, 1.71119225025177, 1.4625779390335083, 1.6414413452148438, 3.688246488571167, 3.4665136337280273, 2.3001456260681152, 2.8655993938446045, 0.18777112662792206, 0.24441646039485931, 0.2783827781677246, 0.23148246109485626, 0.20626476407051086, 0.15988604724407196, 0.23296287655830383, 0.20702330768108368, 0.21666426956653595, 0.15386918187141418, 0.25917065143585205, 0.2595071494579315, 0.1759684830904007, 0.20715531706809998, 0.21643516421318054, 0.20809508860111237, 0.2754974067211151, 0.18720687925815582, 0.292695015668869, 0.2047213762998581, 0.2524997293949127, 0.23631052672863007, 0.2633112370967865, 0.26970213651657104, 0.2854554057121277, 0.22069033980369568, 0.2816808223724365, 0.2042073756456375, 0.21718108654022217, 0.19948358833789825, 0.26968541741371155, 0.21943797171115875, 0.234756201505661, 0.17671577632427216, 0.23914207518100739, 0.22218963503837585, 0.2728915810585022, 0.163825124502182, 0.23769965767860413, 0.2770172357559204, 0.24789157509803772, 0.2028016448020935, 0.2800953686237335, 0.2470066249370575, 0.207948699593544, 0.24494004249572754, 0.23496900498867035, 0.23719075322151184, 0.2140427976846695, 0.1918991357088089, 0.19150809943675995, 0.1886044591665268, 0.24930691719055176, 0.2734930217266083, 0.2572386562824249, 0.22453944385051727, 0.22436189651489258, 0.23805445432662964, 0.21209383010864258, 0.23197126388549805, 0.29520756006240845, 0.25225841999053955, 0.17962434887886047, 0.2657194435596466, 0.21490764617919922, 0.3125496506690979, 0.25537315011024475, 0.32075515389442444, 0.26780906319618225, 0.23985157907009125, 0.23594798147678375, 0.2819077670574188, 0.2219199687242508, 0.2146606743335724, 0.20928266644477844, 0.15957334637641907, 0.16143174469470978, 0.21059779822826385, 0.2385449856519699, 0.22579924762248993, 0.18725751340389252, 0.2269117683172226, 0.22835548222064972, 0.23640620708465576, 0.24177058041095734, 0.17181070148944855, 0.22578628361225128, 0.2685249149799347, 0.18446898460388184, 0.19705426692962646, 0.20723092555999756, 0.21684673428535461, 0.2073614001274109, 0.2731616795063019, 0.2910448908805847, 0.240813747048378, 0.22835631668567657, 0.21746166050434113, 0.26222744584083557, 0.22876876592636108, 0.26239216327667236, 0.18777206540107727, 0.2087181657552719, 0.32149258255958557, 0.1753014326095581, 0.22003157436847687, 0.216251403093338, 0.15041716396808624, 0.25983795523643494, 0.24493877589702606, 0.21656917035579681, 0.23298697173595428, 0.23206952214241028, 0.19596821069717407, 0.19555111229419708, 0.22881276905536652, 0.27391013503074646, 0.24831520020961761, 0.2125723659992218, 0.23352721333503723, 0.2041039615869522, 0.2166605293750763, 0.26525989174842834, 0.22611601650714874, 0.21254153549671173, 0.21292074024677277, 0.2448926866054535, 0.3073979616165161, 0.1986837387084961, 0.21559126675128937, 0.22260981798171997, 0.21952159702777863, 0.2325308620929718, 0.21273691952228546, 0.23416228592395782, 0.1738000512123108, 0.26012665033340454, 0.2517002820968628, 0.22964556515216827, 0.2043503075838089, 0.23754321038722992, 0.31075599789619446, 0.26379886269569397, 0.1838090419769287, 0.23404933512210846, 0.2727614641189575, 0.24657294154167175, 0.26132452487945557, 0.2478131800889969, 0.1860874891281128, 0.2432016283273697, 0.2535550594329834, 0.18828916549682617, 0.3225761353969574, 0.20713432133197784, 0.24546419084072113, 0.2599760890007019, 0.1990080177783966, 0.20430047810077667, 0.25145530700683594, 0.29604482650756836, 0.2196028083562851, 0.23849108815193176, 0.1371684968471527, 0.17628386616706848, 0.23675918579101562, 0.26023510098457336, 0.17406173050403595, 0.196638822555542, 0.26828494668006897, 0.18502670526504517, 0.2538512051105499, 0.26950904726982117, 0.19961202144622803, 0.23210212588310242, 0.2516481578350067, 0.19364894926548004, 0.2734305262565613, 0.2062710076570511, 0.1902344971895218, 0.2491014450788498, 0.2405930608510971, 0.1869647055864334, 0.25323885679244995, 0.19362704455852509, 0.21141162514686584, 0.2028951197862625, 0.2632176876068115, 0.19214074313640594, 0.21266712248325348, 0.2648357152938843, 0.23360808193683624, 0.2269500494003296, 0.2788982689380646, 0.2790696322917938, 0.24670051038265228, 0.22641021013259888, 0.25319376587867737, 0.2549300789833069, 0.20713959634304047, 0.1633581519126892, 0.24004626274108887, 0.2094116508960724, 0.3239285945892334, 0.22319012880325317, 0.19426079094409943, 0.19128650426864624, 0.26912859082221985, 0.2429790496826172, 0.24738942086696625, 0.2592674493789673, 0.20425429940223694, 0.2309686541557312, 0.26695936918258667, 0.15942907333374023, 0.21433380246162415, 0.1972259283065796, 0.1765272170305252, 0.27053001523017883, 0.215798482298851, 0.21676428616046906, 0.27149689197540283, 0.2006191462278366, 0.23210056126117706, 0.23257571458816528, 0.2066156268119812, 0.30998268723487854, 0.22007890045642853, 0.23595502972602844, 0.2173789143562317, 0.22516456246376038, 0.18763692677021027, 0.2362966239452362, 0.2106660008430481, 0.26129817962646484, 0.17660106718540192, 0.26506659388542175, 0.2143648862838745, 0.3178821802139282, 0.23571781814098358, 0.2689000964164734, 0.28259408473968506, 0.25846514105796814, 0.260616660118103, 0.22648084163665771, 0.23100875318050385, 0.2357776165008545, 0.2848314046859741, 0.20992721617221832, 0.2708789110183716, 0.22084999084472656, 0.23550143837928772, 0.2069365233182907, 0.21670103073120117, 0.23099178075790405, 0.22304058074951172, 0.23062960803508759, 0.24899551272392273, 0.23074619472026825, 0.21679751574993134, 0.20206721127033234, 0.20780318975448608, 0.21258670091629028, 0.20840048789978027, 0.18526172637939453, 0.22163815796375275, 0.3058167099952698, 0.22262631356716156, 0.22271394729614258, 0.19380319118499756, 0.2226184457540512, 0.2411196082830429, 0.19885453581809998, 0.2218690663576126, 0.29011937975883484, 0.23444922268390656, 0.2263597697019577, 0.16656909883022308, 0.2697542905807495, 0.25728222727775574, 0.23606978356838226, 0.23772761225700378, 0.18838107585906982, 0.23205192387104034, 0.2732730507850647, 0.20173217356204987, 0.2594728469848633, 0.22501921653747559, 0.22614939510822296, 0.26047489047050476, 0.22679488360881805, 0.22731509804725647, 0.24475662410259247, 0.21399323642253876, 0.19723333418369293, 0.2074396014213562, 0.30303698778152466, 0.20260629057884216, 0.20585936307907104, 0.20194464921951294, 1.7874071598052979, 2.0301496982574463, 3.5104267597198486, 2.8413891792297363, 2.6474156379699707, 1.6355535984039307, 2.676607608795166, 3.652916431427002, 1.732725739479065, 2.732103109359741, 3.0581371784210205, 2.8042514324188232, 1.9894212484359741, 2.606156587600708, 1.8034194707870483, 3.04770827293396, 2.096170663833618, 3.5949065685272217, 3.0097668170928955, 1.6002570390701294, 2.571049690246582, 3.561709403991699, 2.2525739669799805, 3.045591354370117, 2.7190017700195312, 1.7747325897216797, 2.608474016189575, 2.637127637863159, 1.7667165994644165, 2.608792304992676, 1.5674129724502563, 2.6567463874816895, 2.23954701423645, 3.4338390827178955, 2.0580711364746094, 2.775364398956299, 2.6590051651000977, 2.7575478553771973, 3.921780824661255, 2.577486515045166, 2.074185371398926, 1.7759718894958496, 3.1914825439453125, 2.8645122051239014, 3.0286364555358887, 1.6858618259429932, 2.146008014678955, 2.5933728218078613, 2.8296215534210205, 1.7236156463623047, 2.3135581016540527, 2.2524354457855225, 2.976985454559326, 2.8064231872558594, 2.973767042160034, 2.733137845993042, 2.505845785140991, 2.3924238681793213, 2.2458455562591553, 2.0209779739379883, 2.0133605003356934, 3.5908138751983643, 3.2856392860412598, 2.942490816116333, 3.9539482593536377, 3.011505603790283, 2.038486957550049, 2.6376330852508545, 1.988955020904541, 1.6458408832550049, 1.3387283086776733, 1.8427367210388184, 2.6900036334991455, 2.880742311477661, 1.755710244178772, 3.3748726844787598, 2.6721458435058594, 2.019792318344116, 2.4076929092407227, 2.943838357925415, 2.12182879447937, 3.6940789222717285, 2.484951972961426, 1.5868191719055176, 2.8368606567382812, 2.4094128608703613, 3.5511512756347656, 2.117030143737793, 2.704298734664917, 2.537398099899292, 3.125391721725464, 1.9168998003005981, 1.9108326435089111, 2.331385850906372, 2.4247758388519287, 3.2834887504577637, 2.6728692054748535, 4.225783824920654, 2.6687798500061035, 2.0720198154449463, 2.1631929874420166, 3.0235595703125, 3.462062358856201, 2.570521831512451, 2.1765196323394775, 2.789313316345215, 1.9894747734069824, 1.7173881530761719, 3.5979220867156982, 2.5650417804718018, 2.0950186252593994, 2.2482235431671143, 2.6299400329589844, 2.4102554321289062, 2.2692365646362305, 2.711320161819458, 2.774550676345825, 2.8375346660614014, 1.7989513874053955, 2.4926517009735107, 2.094529151916504, 2.29331636428833, 2.015287399291992, 1.898659586906433, 2.2896859645843506, 2.7685840129852295, 3.491715669631958, 2.509913682937622, 3.650466203689575, 1.7834159135818481, 1.654927134513855, 2.952502489089966, 2.662187099456787, 2.182155132293701, 2.4711809158325195, 2.344395637512207, 3.297522783279419, 1.9913963079452515, 2.3671281337738037, 3.0854275226593018, 2.4691264629364014, 2.7009799480438232, 2.6021666526794434, 2.1495046615600586, 2.845759868621826, 2.5401971340179443, 3.2024974822998047, 3.3314807415008545, 2.1663894653320312, 3.548375368118286, 2.3223941326141357, 2.283046245574951, 1.8900729417800903, 2.9697494506835938, 1.7347582578659058, 2.174281358718872, 1.9136110544204712, 3.2180888652801514, 2.2033257484436035, 3.0110647678375244, 3.2517223358154297, 1.973272681236267, 2.626661539077759, 1.8211135864257812, 2.2437374591827393, 2.9596710205078125, 1.8201055526733398, 2.858144760131836, 1.5971794128417969, 1.5581464767456055, 2.4205124378204346, 2.654285192489624, 2.9463391304016113, 1.5075002908706665, 1.5281683206558228, 1.954070806503296, 2.594905376434326, 3.5141313076019287, 2.0749921798706055, 1.65774405002594, 2.221723794937134, 2.5577409267425537, 2.947307586669922, 1.7257537841796875, 3.0610363483428955, 2.3349814414978027, 3.2953789234161377, 2.9081578254699707, 3.2651889324188232, 2.0224380493164062, 2.600651264190674, 2.4341979026794434, 1.590081810951233, 2.486575126647949, 2.3051514625549316, 3.584205150604248, 2.3270349502563477, 1.6828627586364746, 2.6055023670196533, 2.461663246154785, 2.8052926063537598, 2.6384477615356445, 3.114689350128174, 1.7447130680084229, 3.4684131145477295, 3.2600395679473877, 2.3302788734436035, 3.8703112602233887, 1.968364953994751, 3.0541939735412598, 2.5949273109436035, 2.513861894607544, 2.59942626953125, 1.3081319332122803, 2.6122570037841797, 2.219407081604004, 2.1731441020965576, 1.9888267517089844, 2.712592363357544, 2.4488625526428223, 2.3924989700317383, 2.7388343811035156, 2.631176710128784, 2.3531830310821533, 2.569672107696533, 3.073315382003784, 1.6416021585464478, 1.942995309829712, 2.6203465461730957, 2.793076753616333, 3.5666496753692627, 3.0578417778015137, 3.395840883255005, 2.1667394638061523, 2.2815029621124268, 1.6171646118164062, 2.6483561992645264, 1.738736867904663, 2.4787838459014893, 2.795790433883667, 2.857327699661255, 1.2914788722991943, 2.7103633880615234, 2.1038012504577637, 2.5384411811828613, 2.138184070587158, 2.160196542739868, 2.673922061920166, 2.639954090118408, 2.67020320892334, 2.0884194374084473, 3.4290122985839844, 1.9354937076568604, 3.5636544227600098, 3.040513277053833, 2.8050262928009033, 3.376784563064575, 2.6852455139160156, 3.1363365650177, 1.7408913373947144, 2.0094892978668213, 2.7668545246124268, 1.9625606536865234, 2.9926159381866455, 2.6207516193389893, 3.7794816493988037, 2.49039626121521, 1.8224096298217773, 2.177914619445801, 2.6525425910949707, 2.9243245124816895, 2.602729320526123, 2.8678219318389893, 2.4926674365997314, 3.9626922607421875, 2.937786102294922, 2.790062427520752, 1.9178948402404785, 1.719973087310791, 1.7646963596343994, 3.03295636177063, 2.915259599685669, 2.728654623031616, 2.6877527236938477, 1.9330358505249023, 2.240907669067383, 2.4382829666137695, 2.3782615661621094, 3.56803822517395, 1.7398467063903809, 2.791081428527832, 2.18674373626709, 2.6130077838897705, 2.2910120487213135, 3.3223366737365723, 2.434786081314087, 1.6563634872436523, 2.1112661361694336, 3.4348602294921875, 1.912771224975586, 303.237060546875, 122.80522918701172, 392.7469177246094, 141.51898193359375, 409.3822326660156, 298.34619140625, 96.84136199951172, 138.3743896484375, 573.8473510742188, 137.3114013671875, 172.1425018310547, 212.6951141357422, 224.23301696777344, 528.485107421875, 252.84378051757812, 63.18372344970703, 180.3533935546875, 477.984375, 74.80272674560547, 112.43511199951172, 228.9895782470703, 63.5281982421875, 101.97967529296875, 151.32464599609375, 191.2696075439453, 158.92410278320312, 221.56507873535156, 217.19464111328125, 223.2138671875, 88.37804412841797, 213.4126739501953, 148.5721435546875, 97.92362976074219, 217.24371337890625, 209.12913513183594, 151.64923095703125, 678.6842041015625, 99.99148559570312, 185.1833953857422, 84.31707763671875, 178.75819396972656, 115.9208984375, 178.84893798828125, 83.05043029785156, 227.3944854736328, 238.361328125, 168.57357788085938, 119.11297607421875, 137.07823181152344, 278.9639892578125, 49.98065185546875, 239.69053649902344, 249.75929260253906, 126.7538833618164, 72.00992584228516, 141.10997009277344, 193.6525421142578, 136.93072509765625, 215.97080993652344, 197.8535919189453, 360.9940185546875, 47.3409423828125, 89.03170776367188, 69.42767333984375, 126.98876953125, 237.11865234375, 268.03729248046875, 156.66790771484375, 119.51791381835938, 379.5919494628906, 268.450439453125, 70.21746826171875, 172.99951171875, 145.94287109375, 240.54055786132812, 234.97607421875, 55.95892333984375, 74.34765625, 142.823974609375, 119.85558319091797, 117.35321044921875, 143.0576934814453, 90.98491668701172, 102.98062133789062, 61.572635650634766, 209.3616943359375, 266.21636962890625, 261.2549133300781, 59.80305862426758, 191.89874267578125, 55.18354415893555, 127.99869537353516, 194.8936309814453, 181.24827575683594, 294.872802734375, 185.60675048828125, 561.6832885742188, 118.51300811767578, 384.845703125, 379.0484924316406, 72.0418472290039, 274.25006103515625, 91.19168090820312, 107.66509246826172, 218.2901153564453, 314.62152099609375, 72.02432250976562, 147.66676330566406, 173.6165771484375, 106.45265197753906, 300.705810546875, 170.07180786132812, 99.90055084228516, 91.77544403076172, 112.36013793945312, 124.80482482910156, 176.24925231933594, 127.19103240966797, 79.9061279296875, 143.50057983398438, 146.549072265625, 194.31211853027344, 337.825927734375, 114.8798599243164, 90.43263244628906, 231.02978515625, 186.96923828125, 156.3355255126953, 265.18377685546875, 146.7646484375, 420.256591796875, 44.955623626708984, 40.559226989746094, 311.0826416015625, 63.6732177734375, 572.350341796875, 61.3759765625, 320.52484130859375, 135.49559020996094, 45.575252532958984, 618.73583984375, 109.91978454589844, 228.06944274902344, 301.323974609375, 252.0574493408203, 280.94964599609375, 151.0294647216797, 94.21060180664062, 137.87852478027344, 224.13397216796875, 126.01068115234375, 83.2138671875, 266.31219482421875, 165.2669677734375, 200.0837860107422, 147.7696990966797, 180.8972930908203, 246.31320190429688, 403.3592224121094, 99.08451080322266, 227.61546325683594, 349.6722717285156, 102.70716857910156, 315.00537109375, 336.8090515136719, 100.65576171875, 105.67599487304688, 255.7195587158203, 189.97433471679688, 62.48089599609375, 573.6680908203125, 322.1785583496094, 105.5892333984375, 209.2274932861328, 111.21063232421875, 214.0205078125, 274.62225341796875, 103.18193054199219, 186.8499755859375, 306.5127258300781, 134.78793334960938, 95.509521484375, 293.88629150390625, 229.052490234375, 101.72220611572266, 247.33108520507812, 308.7469177246094, 97.0008544921875, 269.3489990234375, 296.30035400390625, 125.31561279296875, 216.54405212402344, 150.89630126953125, 176.87249755859375, 125.10314178466797, 143.9637451171875, 403.54437255859375, 128.2246856689453, 101.86878967285156, 347.9229736328125, 353.664794921875, 66.56414794921875, 186.8407745361328, 118.53527069091797, 94.11677551269531, 118.77082824707031, 136.90567016601562, 121.66087341308594, 391.9585876464844, 145.3841552734375, 171.2875518798828, 318.42205810546875, 70.90670776367188, 146.3587646484375, 246.2548370361328, 316.799560546875, 101.62574005126953, 101.97802734375, 194.2657012939453, 200.27505493164062, 261.7310791015625, 170.50753784179688, 148.72525024414062, 60.1259765625, 92.17376708984375, 255.86065673828125, 245.3631134033203, 213.82933044433594, 116.03558349609375, 593.5333251953125, 110.952880859375, 113.30089569091797, 282.119140625, 175.9984130859375, 202.6766815185547, 272.10992431640625, 346.2421875, 380.0099182128906, 154.77359008789062, 214.1878204345703, 276.49365234375, 369.3586120605469, 205.53924560546875, 464.1769104003906, 169.1551513671875, 255.2080841064453, 70.68878936767578, 214.57542419433594, 49.0654296875, 303.8040466308594, 99.00306701660156, 516.8997802734375, 45.83350372314453, 220.31358337402344, 88.24466705322266, 130.3831329345703, 70.67940521240234, 135.544677734375, 320.28289794921875, 99.90196990966797, 93.57584381103516, 119.97142028808594, 159.7088623046875, 256.6511535644531, 125.53192138671875, 131.30853271484375, 182.1219024658203, 347.4523620605469, 35.831085205078125, 60.949462890625, 185.74575805664062, 100.18560028076172, 261.2044677734375, 193.85986328125, 157.259765625, 231.94287109375, 115.9388427734375, 36.295166015625, 99.05587005615234, 138.3987579345703, 48.480995178222656, 230.4459686279297, 310.74029541015625, 71.79825592041016, 81.00061798095703, 61.72528076171875, 35.98167037963867, 405.630859375, 49.169677734375, 96.75972747802734, 250.3788604736328, 155.3533477783203, 53.78491973876953, 337.7300720214844, 148.65509033203125, 343.187255859375, 158.3279266357422, 152.27978515625, 111.27469635009766, 313.38214111328125, 1.6072677373886108, 3.0652096271514893, 1.7441664934158325, 1.898844838142395, 2.6279115676879883, 2.764054536819458, 2.438749074935913, 2.093472480773926, 3.095080614089966, 2.329756021499634, 2.6130285263061523, 2.057814598083496, 3.102952241897583, 2.0893406867980957, 2.2934961318969727, 2.424984931945801, 2.432284116744995, 1.9802042245864868, 2.526451587677002, 2.0831761360168457, 2.063511848449707, 1.4762755632400513, 3.3092620372772217, 2.4188880920410156, 1.8699684143066406, 3.275851249694824, 3.2484471797943115, 2.7325737476348877, 2.402449607849121, 3.39078426361084, 2.4534010887145996, 2.1096854209899902, 3.5765647888183594, 3.9616191387176514, 2.3826026916503906, 2.2807724475860596, 2.9271533489227295, 2.1893715858459473, 2.3767824172973633, 2.923478364944458, 2.6612889766693115, 3.414292573928833, 1.659834861755371, 3.642293691635132, 2.775394916534424, 2.723339796066284, 1.886535406112671, 2.457721710205078, 2.2367045879364014, 2.6776721477508545, 3.2213985919952393, 2.581286668777466, 1.5809459686279297, 3.689671516418457, 1.683125376701355, 2.042898654937744, 2.9454071521759033, 3.298175573348999, 2.8464953899383545, 2.480891704559326, 2.969255208969116, 2.059786796569824, 3.7439379692077637, 2.6483561992645264, 3.035407543182373, 1.8241970539093018, 1.372497797012329, 2.0586938858032227, 3.687930107116699, 3.172999143600464, 2.0360281467437744, 2.9151198863983154, 1.912672996520996, 3.1216862201690674, 3.3187437057495117, 1.9188616275787354, 2.8512847423553467, 2.0066885948181152, 1.135014295578003, 2.831134080886841, 2.42145037651062, 2.1479718685150146, 2.3693413734436035, 1.6190942525863647, 2.5045347213745117, 2.8558642864227295, 1.9134550094604492, 2.657816171646118, 2.3996129035949707, 3.181766986846924, 2.871023178100586, 2.36737322807312, 3.001267671585083, 2.8774664402008057, 2.868936061859131, 2.3974075317382812, 2.483351707458496, 3.3365581035614014, 2.438969612121582, 2.173734426498413, 2.086103677749634, 2.7044506072998047, 2.9082860946655273, 2.332876205444336, 3.3267834186553955, 2.704116106033325, 2.3892123699188232, 2.200576066970825, 2.3047475814819336, 3.3291149139404297, 2.0474963188171387, 3.690068244934082, 3.4492557048797607, 1.564626693725586, 2.0255308151245117, 1.8159645795822144, 1.8361238241195679, 3.509406566619873, 2.3110508918762207, 2.813483238220215, 3.8827624320983887, 1.62248957157135, 3.004971504211426, 2.714679479598999, 2.3795294761657715, 1.7937759160995483, 1.9864997863769531, 2.997941732406616, 2.904130220413208, 2.4418253898620605, 3.2535600662231445, 2.619063138961792, 3.4054179191589355, 2.7974064350128174, 2.305177927017212, 3.2473442554473877, 2.135084867477417, 2.3699865341186523, 2.0215868949890137, 2.232856273651123, 1.6951225996017456, 2.885118246078491, 2.1194393634796143, 3.0721676349639893, 3.6199862957000732, 3.0668041706085205, 2.4360897541046143, 3.9235007762908936, 2.6898021697998047, 3.661872148513794, 3.0266711711883545, 2.163231134414673, 1.6494348049163818, 3.11747670173645, 2.1993207931518555, 4.135770320892334, 2.1989946365356445, 3.5876970291137695, 1.7026405334472656, 3.097867250442505, 2.9142065048217773, 2.970752000808716, 2.4001550674438477, 2.4224696159362793, 2.148850440979004, 2.524632453918457, 1.7524994611740112, 2.2028894424438477, 2.464729070663452, 1.6009801626205444, 2.937595844268799, 1.8858709335327148, 2.746209144592285, 2.4988222122192383, 2.6870291233062744, 2.2069406509399414, 2.2332260608673096, 3.10922908782959, 1.8587905168533325, 2.997789144515991, 2.4961998462677, 3.4862639904022217, 2.256305694580078, 3.3498191833496094, 2.811586856842041, 2.95676589012146, 3.2170727252960205, 2.2226381301879883, 2.7843239307403564, 2.3274688720703125, 2.149993658065796, 2.031738758087158, 2.960252285003662, 2.0031261444091797, 2.14088773727417, 2.579301118850708, 3.294095277786255, 2.432088613510132, 1.8443336486816406, 2.0234506130218506, 2.907850980758667, 4.153925895690918, 2.564863920211792, 2.79984712600708, 1.6644301414489746, 2.0301871299743652, 4.022627353668213, 2.635815382003784, 2.4546027183532715, 2.607112407684326, 2.0851385593414307, 3.9273180961608887, 3.5759594440460205, 2.8685412406921387, 3.0052578449249268, 1.8568819761276245, 2.3814191818237305, 2.921403646469116, 2.842681884765625, 2.930049180984497, 3.7040300369262695, 2.925828218460083, 2.8138017654418945, 2.704669237136841, 2.64340877532959, 1.9912575483322144, 3.3116519451141357, 2.663926362991333, 2.476715564727783, 3.1953043937683105, 1.7425718307495117, 1.8934431076049805, 3.5796008110046387, 2.214081287384033, 3.5818092823028564, 3.508516788482666, 2.24271297454834, 2.6256909370422363, 2.49636173248291, 2.674481153488159, 2.0911455154418945, 3.618802309036255, 3.15356183052063, 2.3498904705047607, 2.3833847045898438, 3.5554234981536865, 2.9090416431427, 1.9387401342391968, 2.3373312950134277, 1.9348320960998535, 3.556473970413208, 1.9112807512283325, 2.2121663093566895, 3.3244848251342773, 2.419947624206543, 2.9593615531921387, 2.7608044147491455, 1.6772854328155518, 2.011350631713867, 1.7920622825622559, 2.7548577785491943, 2.5007662773132324, 2.093379259109497, 2.230844736099243, 3.2603960037231445, 2.9216325283050537, 3.2236011028289795, 3.78337025642395, 1.8315114974975586, 3.11775541305542, 3.6506528854370117, 1.3332704305648804, 1.8370050191879272, 2.9789745807647705, 2.592881441116333, 3.1444637775421143, 1.9151872396469116, 3.1869399547576904, 4.101682662963867, 3.3093442916870117, 2.954859972000122, 1.9666107892990112, 1.613850474357605, 2.5262327194213867, 2.730680465698242, 1.2283517122268677, 2.239130973815918, 2.7250571250915527, 2.615422248840332, 2.1290440559387207, 3.034756660461426, 3.8737003803253174, 3.3656609058380127, 3.2558131217956543, 1.6720616817474365, 3.5700883865356445, 3.534135103225708, 2.62807035446167, 3.0133891105651855, 1.6374787092208862, 0.26402294635772705, 0.23428760468959808, 0.2043544352054596, 0.22830379009246826, 0.2577812075614929, 0.24411174654960632, 0.21087601780891418, 0.2404477298259735, 0.24337026476860046, 0.15658949315547943, 0.24701499938964844, 0.23811271786689758, 0.2619974911212921, 0.254770964384079, 0.22048698365688324, 0.3081945478916168, 0.16776099801063538, 0.2790696620941162, 0.1820615530014038, 0.25316113233566284, 0.177564337849617, 0.21499009430408478, 0.22726435959339142, 0.20965611934661865, 0.23808161914348602, 0.2317713052034378, 0.20645806193351746, 0.20439600944519043, 0.30045202374458313, 0.225882887840271, 0.28586864471435547, 0.19200801849365234, 0.17400169372558594, 0.26712679862976074, 0.21972085535526276, 0.20469141006469727, 0.25434747338294983, 0.1882171779870987, 0.19230468571186066, 0.2260291427373886, 0.2154342532157898, 0.23651309311389923, 0.22882170975208282, 0.24253599345684052, 0.18987968564033508, 0.23171605169773102, 0.1438351273536682, 0.22556611895561218, 0.17997026443481445, 0.20085692405700684, 0.21236388385295868, 0.26378652453422546, 0.27645164728164673, 0.14644213020801544, 0.20131400227546692, 0.28129053115844727, 0.15686285495758057, 0.2741624414920807, 0.2707955837249756, 0.22882382571697235, 0.24797017872333527, 0.2227896898984909, 0.22086171805858612, 0.20264315605163574, 0.23431049287319183, 0.3042900562286377, 0.3537116050720215, 0.19186225533485413, 0.22500284016132355, 0.24487410485744476, 0.2141643464565277, 0.30104416608810425, 0.23049555718898773, 0.24554747343063354, 0.24311070144176483, 0.20980538427829742, 0.24052833020687103, 0.23574894666671753, 0.27007243037223816, 0.201409712433815, 0.18557330965995789, 0.2439141422510147, 0.2597344219684601, 0.23307251930236816, 0.1680295765399933, 0.27839118242263794, 0.16189153492450714, 0.2607651948928833, 0.2335725873708725, 0.277059406042099, 0.2017824947834015, 0.22688621282577515, 0.23178519308567047, 0.23155689239501953, 0.20700892806053162, 0.2358061969280243, 0.2977887690067291, 0.2744315564632416, 0.25950661301612854, 0.3068980574607849, 0.2054145336151123, 0.19632720947265625, 0.2862620949745178, 0.3141081631183624, 0.18716125190258026, 0.2919631600379944, 0.23507240414619446, 0.16730856895446777, 0.16378368437290192, 0.2662542760372162, 0.24360810220241547, 0.24866187572479248, 0.22023585438728333, 0.2345810979604721, 0.19569221138954163, 0.22903206944465637, 0.20545874536037445, 0.1904672533273697, 0.297194242477417, 0.20896756649017334, 0.302187979221344, 0.34041252732276917, 0.2358274757862091, 0.26234811544418335, 0.2940298318862915, 0.22061538696289062, 0.23110978305339813, 0.17823441326618195, 0.23480486869812012, 0.25106680393218994, 0.21856284141540527, 0.26456522941589355, 0.17335708439350128, 0.22800233960151672, 0.24572573602199554, 0.3031170964241028, 0.2318534404039383, 0.3025885820388794, 0.21778610348701477, 0.22863200306892395, 0.24785199761390686, 0.20754113793373108, 0.2536320090293884, 0.2294294238090515, 0.22022366523742676, 0.2599327862262726, 0.18716378509998322, 0.2519482672214508, 0.24667876958847046, 0.25592079758644104, 0.22519345581531525, 0.16312207281589508, 0.19075076282024384, 0.20914117991924286, 0.13299253582954407, 0.25904810428619385, 0.22689563035964966, 0.3021758198738098, 0.20941893756389618, 0.25185051560401917, 0.2444988340139389, 0.2158048152923584, 0.2644478976726532, 0.10668546706438065, 0.2139284610748291, 0.2083531767129898, 0.18078991770744324, 0.20920893549919128, 0.19708125293254852, 0.22724322974681854, 0.23372070491313934, 0.2282978892326355, 0.22040142118930817, 0.2516852617263794, 0.1876319795846939, 0.2525840401649475, 0.26988065242767334, 0.3024260699748993, 0.26375189423561096, 0.3069513142108917, 0.2290828973054886, 0.26822277903556824, 0.17182467877864838, 0.2243495136499405, 0.3010713756084442, 0.1941913217306137, 0.25967857241630554, 0.24412840604782104, 0.21437270939350128, 0.25285232067108154, 0.20717290043830872, 0.24128615856170654, 0.2059415727853775, 0.243660107254982, 0.1949390321969986, 0.24011138081550598, 0.25487807393074036, 0.2820134460926056, 0.2525010108947754, 0.2888803482055664, 0.2354886531829834, 0.20240630209445953, 0.17998091876506805, 0.2310672551393509, 0.2766638398170471, 0.26107412576675415, 0.22013351321220398, 0.2195022851228714, 0.24805016815662384, 0.22319230437278748, 0.22746171057224274, 0.22736291587352753, 0.21253681182861328, 0.2807003855705261, 0.25398433208465576, 0.2806374430656433, 0.23877082765102386, 0.1897987574338913, 0.22953282296657562, 0.25993263721466064, 0.19513152539730072, 0.2376481592655182, 0.27088662981987, 0.28953826427459717, 0.19083113968372345, 0.22694389522075653, 0.23886914551258087, 0.23720601201057434, 0.22839732468128204, 0.24348777532577515, 0.18876315653324127, 0.17677268385887146, 0.19913193583488464, 0.22613975405693054, 0.23032523691654205, 0.2413407266139984, 0.2498488575220108, 0.23346741497516632, 0.23906749486923218, 0.21001502871513367, 0.1624370515346527, 0.22425055503845215, 0.2795753479003906, 0.25076982378959656, 0.16056391596794128, 0.22291414439678192, 0.20028866827487946, 0.19570010900497437, 0.22504399716854095, 0.2185603231191635, 0.1824522763490677, 0.2808435261249542, 0.21268656849861145, 0.23953764140605927, 0.23025894165039062, 0.19308659434318542, 0.2603682279586792, 0.19411490857601166, 0.21433177590370178, 0.22956740856170654, 0.24315284192562103, 0.2577085793018341, 0.26333320140838623, 0.3019092381000519, 0.24135930836200714, 0.24159923195838928, 0.21955092251300812, 0.16614943742752075, 0.2533442974090576, 0.14040836691856384, 0.1634732335805893, 0.2511543333530426, 0.23102092742919922, 0.23492780327796936, 0.2370705008506775, 0.18150383234024048, 0.2247297167778015, 0.2697097063064575, 0.19536323845386505, 0.25782540440559387, 0.21684463322162628, 0.16676375269889832, 0.2129485011100769, 0.25953131914138794, 0.25453421473503113, 0.24654756486415863, 0.18681636452674866, 0.2585775554180145, 0.2718086838722229, 0.23188498616218567, 0.24857379496097565, 0.22246906161308289, 0.2517877519130707, 0.26522934436798096, 0.20480471849441528, 0.2640571892261505, 0.22290682792663574, 0.20521391928195953, 0.28319090604782104, 0.21337220072746277, 2.4534289836883545, 3.047950029373169, 1.488569736480713, 3.2828891277313232, 3.4903831481933594, 3.0992767810821533, 2.07743239402771, 2.14762282371521, 1.9908329248428345, 3.0918915271759033, 3.110006332397461, 1.750577449798584, 2.133765459060669, 3.209346294403076, 3.528123617172241, 2.2587013244628906, 3.9625446796417236, 3.7601406574249268, 2.9629604816436768, 2.257244110107422, 2.5891363620758057, 1.8908579349517822, 1.6724951267242432, 1.979334831237793, 3.5385472774505615, 2.7064671516418457, 2.583402633666992, 2.315938711166382, 3.3372318744659424, 1.9619375467300415, 2.4239025115966797, 3.056412935256958, 2.695798873901367, 1.5252033472061157, 3.5741565227508545, 2.5902092456817627, 2.197380542755127, 2.021017074584961, 2.862523078918457, 2.530014991760254, 2.6251604557037354, 2.7880449295043945, 1.9795207977294922, 3.4071121215820312, 2.5298235416412354, 2.50575590133667, 2.8856594562530518, 2.9372270107269287, 2.687424898147583, 3.1901497840881348, 1.9645094871520996, 3.0874035358428955, 3.5276131629943848, 3.06107234954834, 2.2178778648376465, 1.788053274154663, 3.369509696960449, 3.9133732318878174, 2.2313101291656494, 2.1569454669952393, 3.9984593391418457, 3.283565044403076, 4.0626397132873535, 1.9380346536636353, 2.46037220954895, 4.1142730712890625, 1.992798089981079, 2.3904366493225098, 1.7278121709823608, 3.116131544113159, 2.9789111614227295, 2.652205228805542, 1.6743818521499634, 1.8964895009994507, 2.285473346710205, 2.7773988246917725, 3.367037296295166, 2.186882257461548, 2.8280868530273438, 1.6328481435775757, 1.7620737552642822, 1.9666146039962769, 3.3076794147491455, 3.029582977294922, 1.6530863046646118, 3.081166982650757, 1.5591799020767212, 1.9795546531677246, 2.29258394241333, 3.322512149810791, 3.5415074825286865, 2.568751096725464, 2.4573681354522705, 3.072516441345215, 2.8894078731536865, 2.7280220985412598, 2.147540330886841, 2.0029349327087402, 3.387411117553711, 1.971026062965393, 2.004570245742798, 1.8897408246994019, 3.1171114444732666, 2.121368169784546, 2.4691128730773926, 3.9061481952667236, 2.7882027626037598, 2.542515754699707, 2.5085747241973877, 2.5883870124816895, 3.5074737071990967, 1.9988861083984375, 3.2870824337005615, 2.29007887840271, 2.033860206604004, 3.553494691848755, 3.1369094848632812, 2.7577884197235107, 2.67193603515625, 2.568535327911377, 2.9497692584991455, 1.7905371189117432, 3.485245943069458, 2.384180784225464, 2.7254960536956787, 3.3327255249023438, 2.9002151489257812, 2.7463347911834717, 3.6233761310577393, 3.2891628742218018, 2.169863700866699, 1.8056234121322632, 1.9538875818252563, 2.5504918098449707, 2.5988247394561768, 3.4530041217803955, 2.5305087566375732, 2.2161917686462402, 3.2241528034210205, 2.7568981647491455, 3.376284599304199, 1.6360549926757812, 1.7511227130889893, 3.3754940032958984, 1.9164186716079712, 2.1746737957000732, 2.790361166000366, 3.876145601272583, 1.8643851280212402, 2.969172716140747, 2.826603412628174, 3.2769711017608643, 2.1021859645843506, 2.5177507400512695, 2.9659721851348877, 2.981013536453247, 1.8983803987503052, 3.2192134857177734, 2.099371910095215, 2.6834921836853027, 1.879478096961975, 2.4686226844787598, 3.489516019821167, 3.9544944763183594, 2.459686279296875, 2.280923366546631, 2.420820713043213, 2.2505500316619873, 1.8145555257797241, 3.4851274490356445, 3.3677074909210205, 2.5978081226348877, 3.440255880355835, 2.5234909057617188, 1.9672789573669434, 2.9303231239318848, 3.3273227214813232, 2.6232662200927734, 2.4635157585144043, 2.409266233444214, 3.138195037841797, 2.7380998134613037, 1.9682581424713135, 2.398991107940674, 2.5031862258911133, 2.1485683917999268, 2.9897027015686035, 3.1088707447052, 1.721800446510315, 3.1516692638397217, 1.6675478219985962, 2.5669121742248535, 2.2386415004730225, 2.1222755908966064, 3.8273720741271973, 2.4806137084960938, 3.1538472175598145, 1.7947040796279907, 2.083726644515991, 4.170069694519043, 2.2408018112182617, 2.259190082550049, 2.963247060775757, 2.8176379203796387, 3.0362846851348877, 1.9654461145401, 2.8716869354248047, 2.1757216453552246, 3.181549072265625, 1.7941231727600098, 2.552832841873169, 2.954926013946533, 3.0675857067108154, 2.5709097385406494, 2.858940601348877, 1.885156512260437, 3.2993409633636475, 2.3653268814086914, 2.926111936569214, 2.0885634422302246, 1.695656418800354, 2.5193381309509277, 2.3506686687469482, 2.350431442260742, 1.9509423971176147, 2.3786232471466064, 3.782440185546875, 1.925573706626892, 1.9875177145004272, 1.9240972995758057, 3.4578938484191895, 2.095400810241699, 3.4569003582000732, 1.9243639707565308, 1.903631567955017, 2.3669533729553223, 2.7078938484191895, 2.568603992462158, 1.729378342628479, 2.7481436729431152, 3.3709194660186768, 3.3913683891296387, 2.958686113357544, 3.2660439014434814, 2.700946569442749, 2.0122804641723633, 1.5134092569351196, 1.530886173248291, 3.6547977924346924, 2.5260939598083496, 2.9795620441436768, 3.5954394340515137, 1.9497697353363037, 3.1683549880981445, 1.7612797021865845, 2.330700635910034, 4.146421909332275, 2.0234222412109375, 3.163966655731201, 2.753108263015747, 2.3740835189819336, 2.8706417083740234, 2.8285298347473145, 3.000453233718872, 2.424160957336426, 2.8160388469696045, 2.8453850746154785, 2.3437488079071045, 2.1752023696899414, 2.48738431930542, 2.4627270698547363, 3.33024525642395, 3.0827267169952393, 2.666050434112549, 2.5184326171875, 1.8090206384658813, 2.239806652069092, 2.007270097732544, 2.5381009578704834, 3.5866692066192627, 1.448219895362854, 1.9995123147964478, 2.2209177017211914, 2.867656707763672, 2.235443592071533, 1.7613989114761353, 2.937934160232544, 2.7891266345977783, 2.5416853427886963, 1.590375304222107, 2.4038941860198975, 2.329493999481201, 1.962624430656433, 2.2472593784332275, 2.716644763946533, 2.022782325744629, 2.5792698860168457, 2.2570950984954834, 3.360989809036255, 3.7509026527404785, 281.1949462890625, 398.26513671875, 118.12296295166016, 157.31427001953125, 39.5977783203125, 85.441650390625, 93.59689331054688, 69.7557144165039, 309.28448486328125, 238.29920959472656, 132.9049530029297, 177.9612274169922, 234.887451171875, 199.91253662109375, 55.332420349121094, 179.92355346679688, 170.32347106933594, 123.30380249023438, 275.6571960449219, 156.80462646484375, 80.41615295410156, 119.60609436035156, 213.9537811279297, 130.8294677734375, 90.36583709716797, 220.7210693359375, 331.8843688964844, 110.05908203125, 102.15692138671875, 93.27690887451172, 261.12518310546875, 299.7792663574219, 217.8424530029297, 233.27403259277344, 41.57044219970703, 240.26817321777344, 133.6169891357422, 96.72588348388672, 155.73597717285156, 260.0129699707031, 162.4857177734375, 70.73162841796875, 184.5408935546875, 204.1140899658203, 310.1776428222656, 132.9583740234375, 289.34832763671875, 115.38927459716797, 52.51063537597656, 296.5004577636719, 87.62469482421875, 157.03207397460938, 273.5641784667969, 283.99908447265625, 177.33966064453125, 184.90480041503906, 64.35272216796875, 124.41944122314453, 111.19699096679688, 156.27259826660156, 246.8875274658203, 447.2716369628906, 422.3348388671875, 87.51654052734375, 94.63400268554688, 183.68319702148438, 392.0209045410156, 43.1204833984375, 102.13286590576172, 103.30584716796875, 136.99913024902344, 169.92926025390625, 258.1131591796875, 264.8966369628906, 249.3617706298828, 226.85919189453125, 197.30609130859375, 215.32667541503906, 425.018310546875, 65.50440979003906, 285.8616027832031, 70.1536636352539, 69.69110870361328, 179.5516357421875, 334.737060546875, 106.24774169921875, 49.36310577392578, 276.2934265136719, 78.3902587890625, 184.53466796875, 455.5328674316406, 120.85906982421875, 152.62794494628906, 195.22483825683594, 216.7376251220703, 162.48204040527344, 247.37542724609375, 282.8367919921875, 173.67979431152344, 74.963134765625, 170.6482391357422, 139.687255859375, 256.0927734375, 475.83258056640625, 44.97719192504883, 170.5310516357422, 182.160888671875, 127.20380401611328, 139.31439208984375, 205.66233825683594, 197.71505737304688, 38.51785659790039, 493.9365234375, 376.1593322753906, 84.77069091796875, 146.2529296875, 123.88404083251953, 142.96002197265625, 222.69692993164062, 383.15826416015625, 244.44102478027344, 232.9818572998047, 244.82192993164062, 114.27519989013672, 153.00921630859375, 315.9321594238281, 339.6695251464844, 78.84551239013672, 68.28005981445312, 282.5969543457031, 126.48497772216797, 47.4580078125, 179.6156768798828, 279.1961669921875, 139.97592163085938, 194.44268798828125, 316.7337646484375, 98.3416748046875, 175.37744140625, 282.59051513671875, 60.43817138671875, 217.8728790283203, 188.8538818359375, 330.14788818359375, 161.8187713623047, 281.1199035644531, 107.77630615234375, 312.36224365234375, 205.64797973632812, 534.33935546875, 121.68695068359375, 178.3848419189453, 331.6297912597656, 168.6943359375, 275.0685729980469, 256.70330810546875, 319.10565185546875, 140.08685302734375, 254.8935546875, 35.1651611328125, 200.6123046875, 375.1407775878906, 152.5841522216797, 227.8494873046875, 68.73162841796875, 55.12879180908203, 208.62071228027344, 296.6884765625, 150.54498291015625, 120.1131820678711, 142.57952880859375, 131.94639587402344, 206.74188232421875, 67.6434326171875, 376.3361511230469, 189.57456970214844, 81.66253662109375, 248.9500274658203, 81.18657684326172, 330.1466979980469, 212.73202514648438, 283.50634765625, 114.54839324951172, 292.84588623046875, 144.25450134277344, 143.9169921875, 163.8248291015625, 122.27239990234375, 316.47869873046875, 66.05099487304688, 114.35826110839844, 96.1104507446289, 158.5809326171875, 83.70659637451172, 133.38079833984375, 81.85591125488281, 430.2765808105469, 299.5902404785156, 138.92041015625, 387.7176208496094, 313.4990234375, 174.58120727539062, 306.68560791015625, 253.7318115234375, 50.3048095703125, 156.5587921142578, 60.32026672363281, 83.39458465576172, 264.1346130371094, 298.9172668457031, 214.55389404296875, 159.7842559814453, 224.23941040039062, 63.20648193359375, 214.32933044433594, 134.390869140625, 54.19232177734375, 171.87503051757812, 208.68374633789062, 114.60933685302734, 172.27224731445312, 267.34637451171875, 68.6395263671875, 212.3562469482422, 181.05224609375, 134.80316162109375, 240.2630615234375, 299.21917724609375, 210.62664794921875, 163.9337921142578, 243.68182373046875, 98.0068359375, 82.24443817138672, 86.2186279296875, 159.67730712890625, 209.2362518310547, 180.3359375, 305.5892028808594, 94.03846740722656, 463.5460510253906, 236.70721435546875, 227.0772247314453, 128.00439453125, 253.77667236328125, 70.23985290527344, 144.16075134277344, 172.3798065185547, 460.10888671875, 37.02045822143555, 58.388427734375, 65.505615234375, 53.24922561645508, 445.494140625, 178.053466796875, 160.69581604003906, 90.02193450927734, 443.7659912109375, 169.0363311767578, 199.87332153320312, 60.85915756225586, 168.63233947753906, 112.62176513671875, 395.3956604003906, 79.648193359375, 314.3553161621094, 280.1087646484375, 319.9406433105469, 346.6510009765625, 110.09233856201172, 94.2791519165039, 161.60171508789062, 95.39453125, 70.41753387451172, 194.8325958251953, 43.91508865356445, 98.78187561035156, 230.2532958984375, 52.31106185913086, 398.87255859375, 72.37482452392578, 192.79698181152344, 195.19541931152344, 283.64520263671875, 393.9833068847656, 136.10519409179688, 50.25146484375, 350.71710205078125, 94.77508544921875, 456.5304260253906, 32.97076416015625, 179.91751098632812, 49.69347381591797, 188.86672973632812, 203.4828643798828, 93.71527099609375, 131.02328491210938, 320.8436584472656, 172.1070098876953, 100.3011703491211, 123.463623046875, 2.9030778408050537, 3.224743604660034, 2.722186326980591, 3.766047954559326, 2.9961864948272705, 3.1349823474884033, 2.6198413372039795, 1.3802136182785034, 2.500141143798828, 3.17460036277771, 2.061306953430176, 3.962557792663574, 2.85150146484375, 3.875347852706909, 1.61670982837677, 3.637355327606201, 2.826472043991089, 3.1472768783569336, 1.939162254333496, 2.5339555740356445, 2.5539886951446533, 2.3172788619995117, 2.8872218132019043, 1.5822798013687134, 2.470311164855957, 3.164874792098999, 4.0118255615234375, 2.0499019622802734, 2.2720155715942383, 3.9945309162139893, 2.627941846847534, 1.8411611318588257, 2.785832405090332, 2.538525342941284, 1.707100749015808, 1.2686705589294434, 2.5016555786132812, 2.5601134300231934, 2.759617805480957, 2.1434428691864014, 1.7765902280807495, 2.7865495681762695, 1.259730339050293, 2.6400604248046875, 3.72107195854187, 2.5713396072387695, 3.1328325271606445, 1.7906453609466553, 2.9479761123657227, 3.0530712604522705, 1.7529363632202148, 1.8885107040405273, 1.772316813468933, 1.6246795654296875, 2.845719575881958, 3.06520414352417, 3.096615791320801, 1.5976961851119995, 2.7454898357391357, 3.982304573059082, 3.0462892055511475, 1.9468870162963867, 2.9303390979766846, 1.3871947526931763, 2.956252336502075, 3.4843902587890625, 2.3585045337677, 2.192030906677246, 2.5223264694213867, 3.171933889389038, 2.6881515979766846, 2.773796558380127, 2.8432250022888184, 3.296201467514038, 2.3558549880981445, 1.4261022806167603, 2.938960313796997, 1.6819103956222534, 1.0285885334014893, 2.556992530822754, 1.2186235189437866, 2.634324312210083, 2.502061367034912, 2.5773534774780273, 2.5269720554351807, 2.4022417068481445, 3.7351722717285156, 2.6305975914001465, 2.4126763343811035, 1.565638542175293, 2.8324291706085205, 3.296128511428833, 2.32602596282959, 2.994410991668701, 2.793715715408325, 2.132689952850342, 2.5805728435516357, 1.8411186933517456, 3.3645336627960205, 3.0897533893585205, 2.163344621658325, 3.6685900688171387, 2.1837282180786133, 3.202859401702881, 2.620908260345459, 2.198906898498535, 2.750227689743042, 2.100085496902466, 3.264565944671631, 1.8675570487976074, 1.3044538497924805, 2.954455614089966, 2.788973331451416, 2.663451671600342, 3.4898672103881836, 3.021289110183716, 1.732277750968933, 2.0116593837738037, 2.844464063644409, 2.575519323348999, 2.656939744949341, 2.764431953430176, 2.6450324058532715, 3.601408004760742, 3.0751664638519287, 3.218233585357666, 3.517559766769409, 3.0562732219696045, 3.6620190143585205, 3.8790905475616455, 1.9301522970199585, 3.455092191696167, 2.0819718837738037, 3.5936880111694336, 2.3740670680999756, 1.840022087097168, 2.9314980506896973, 3.0686898231506348, 2.044182300567627, 2.088606834411621, 3.386730909347534, 2.9636642932891846, 4.1674089431762695, 2.988469123840332, 3.2401721477508545, 3.935725688934326, 2.174983024597168, 2.596449613571167, 3.275052309036255, 3.2573471069335938, 2.4097816944122314, 2.493760347366333, 3.482560396194458, 2.9478180408477783, 3.1862504482269287, 2.3164758682250977, 2.196988821029663, 2.3491339683532715, 2.063582420349121, 1.7661209106445312, 2.492168426513672, 3.63561749458313, 1.8280915021896362, 2.401972532272339, 3.57845401763916, 3.710106134414673, 3.173966646194458, 2.703638792037964, 3.1080827713012695, 2.7400450706481934, 3.69504451751709, 2.518968343734741, 2.177300453186035, 3.2562496662139893, 3.6021037101745605, 3.486985445022583, 2.696671724319458, 2.0410568714141846, 3.2101640701293945, 2.2111616134643555, 1.9823720455169678, 1.9011849164962769, 2.03720760345459, 3.7987871170043945, 1.5665884017944336, 1.3246450424194336, 1.9561268091201782, 2.701589822769165, 3.379484176635742, 1.5363662242889404, 3.1876156330108643, 2.4450998306274414, 3.306628942489624, 1.8655681610107422, 2.3716681003570557, 2.33634090423584, 3.5515928268432617, 3.750743865966797, 2.661993980407715, 1.546932339668274, 3.3112058639526367, 1.5917812585830688, 2.623795747756958, 2.035378932952881, 2.9831924438476562, 3.783673048019409, 1.5030895471572876, 3.42020583152771, 2.655039072036743, 2.241879463195801, 2.8335015773773193, 2.755659818649292, 2.1232426166534424, 3.0624210834503174, 1.5507692098617554, 1.8807740211486816, 3.5721993446350098, 2.193127155303955, 2.27871036529541, 3.126354932785034, 1.369898796081543, 1.9673528671264648, 2.1916208267211914, 2.8046281337738037, 3.8108983039855957, 2.9161882400512695, 1.6957197189331055, 2.1897497177124023, 3.6024279594421387, 1.914399266242981, 2.9521660804748535, 1.9073927402496338, 2.9760067462921143, 2.807859182357788, 2.257640838623047, 2.0509884357452393, 1.3680541515350342, 3.8362953662872314, 3.1822102069854736, 2.2189972400665283, 3.0252466201782227, 4.033792495727539, 2.4718809127807617, 2.7020492553710938, 2.0254805088043213, 3.4938805103302, 3.763585090637207, 2.6291308403015137, 2.613844633102417, 2.960313081741333, 2.3907878398895264, 2.2181949615478516, 2.002865791320801, 3.107497453689575, 2.149142026901245, 1.9485787153244019, 2.472029447555542, 2.3501827716827393, 2.9394001960754395, 2.648686408996582, 2.336235523223877, 1.9593185186386108, 2.851130247116089, 2.515873908996582, 2.3327646255493164, 3.2462856769561768, 3.1622238159179688, 1.8990427255630493, 3.7284438610076904, 2.1300783157348633, 3.3777897357940674, 2.1118240356445312, 1.4614853858947754, 1.6667646169662476, 3.170638084411621, 3.1267755031585693, 4.200183391571045, 1.9615659713745117, 2.460995674133301, 2.990648031234741, 1.4208974838256836, 2.9206020832061768, 3.3148984909057617, 1.7417302131652832, 2.268047332763672, 2.8178300857543945, 3.291110038757324, 1.7106178998947144, 3.26533842086792, 2.6214282512664795, 2.3860745429992676, 1.894938349723816, 1.9034309387207031, 2.677781343460083, 3.173092842102051, 1.9078543186187744, 2.43827486038208, 1.9654473066329956, 2.5037245750427246, 2.6036767959594727, 0.19808892905712128, 0.2788052260875702, 0.20332086086273193, 0.25907421112060547, 0.27344244718551636, 0.1787559539079666, 0.3079361021518707, 0.21788592636585236, 0.24392028152942657, 0.2244136929512024, 0.25067785382270813, 0.2520168125629425, 0.26740190386772156, 0.26946407556533813, 0.21552741527557373, 0.2570537030696869, 0.2725744843482971, 0.19343045353889465, 0.2650845944881439, 0.2263946533203125, 0.269456684589386, 0.22600296139717102, 0.23538824915885925, 0.16523776948451996, 0.2615632116794586, 0.2636612355709076, 0.2259577512741089, 0.21987418830394745, 0.19370713829994202, 0.24640296399593353, 0.19432295858860016, 0.2794012427330017, 0.2629674971103668, 0.2066088765859604, 0.25037649273872375, 0.18904182314872742, 0.22949691116809845, 0.17443107068538666, 0.19017396867275238, 0.21993803977966309, 0.27695465087890625, 0.1910654455423355, 0.24853618443012238, 0.235030397772789, 0.2163856029510498, 0.265053927898407, 0.2866213321685791, 0.2299899309873581, 0.23128120601177216, 0.19527775049209595, 0.2691749930381775, 0.2775828242301941, 0.2657792568206787, 0.1931806355714798, 0.25811567902565, 0.22500544786453247, 0.20613956451416016, 0.252728134393692, 0.17817698419094086, 0.26079511642456055, 0.16898328065872192, 0.3053751289844513, 0.2015540599822998, 0.25515854358673096, 0.2050083428621292, 0.217610165476799, 0.2260242998600006, 0.2427457571029663, 0.2352292388677597, 0.25217729806900024, 0.27626582980155945, 0.21706180274486542, 0.21825851500034332, 0.22262144088745117, 0.21627332270145416, 0.2677449882030487, 0.17897816002368927, 0.24410860240459442, 0.22463637590408325, 0.2926466763019562, 0.22787204384803772, 0.24297687411308289, 0.33288565278053284, 0.2885039448738098, 0.2360668182373047, 0.2506279945373535, 0.3081151843070984, 0.2662487328052521, 0.22092002630233765, 0.1932809054851532, 0.2570793926715851, 0.2815904915332794, 0.2060074359178543, 0.2510441243648529, 0.2764147222042084, 0.30359023809432983, 0.2374618798494339, 0.17153306305408478, 0.2697814702987671, 0.20101051032543182, 0.2194133847951889, 0.35045188665390015, 0.2708950936794281, 0.19611556828022003, 0.1627921611070633, 0.30805808305740356, 0.25503411889076233, 0.30666136741638184, 0.23898489773273468, 0.24984097480773926, 0.27767714858055115, 0.20838764309883118, 0.23833401501178741, 0.2491980493068695, 0.21878764033317566, 0.2714570164680481, 0.27574023604393005, 0.21009480953216553, 0.24462063610553741, 0.24544207751750946, 0.2572779357433319, 0.2069353461265564, 0.22644580900669098, 0.18392987549304962, 0.1917911320924759, 0.1856088638305664, 0.21563148498535156, 0.26215919852256775, 0.2542972266674042, 0.22517894208431244, 0.18626317381858826, 0.15810464322566986, 0.24261994659900665, 0.2186722457408905, 0.22805404663085938, 0.20101431012153625, 0.21470147371292114, 0.20247304439544678, 0.24533770978450775, 0.24060571193695068, 0.2552569508552551, 0.22452376782894135, 0.17899367213249207, 0.17909474670886993, 0.20012007653713226, 0.27147871255874634, 0.2330174446105957, 0.19449393451213837, 0.28053587675094604, 0.20236942172050476, 0.23516039550304413, 0.27706512808799744, 0.3239423334598541, 0.22165748476982117, 0.25322097539901733, 0.24685651063919067, 0.20939084887504578, 0.24822311103343964, 0.1758904606103897, 0.2797657549381256, 0.19882018864154816, 0.2089824229478836, 0.2652129828929901, 0.2671000063419342, 0.2288925051689148, 0.17286978662014008, 0.25570112466812134, 0.29754266142845154, 0.21294759213924408, 0.1928703337907791, 0.26573753356933594, 0.2560268044471741, 0.2635941803455353, 0.19310198724269867, 0.30382487177848816, 0.2099216729402542, 0.19370998442173004, 0.2472628355026245, 0.20639851689338684, 0.265702486038208, 0.27010563015937805, 0.22839711606502533, 0.2738313674926758, 0.21366176009178162, 0.20597010850906372, 0.2581753432750702, 0.18651540577411652, 0.2803954780101776, 0.22786296904087067, 0.253140926361084, 0.2374797761440277, 0.2503199279308319, 0.2134738564491272, 0.23298068344593048, 0.2986341118812561, 0.28770583868026733, 0.17111797630786896, 0.2106090635061264, 0.2655946910381317, 0.21933211386203766, 0.21395465731620789, 0.2800256609916687, 0.18716014921665192, 0.237141415476799, 0.2236412614583969, 0.2473151683807373, 0.28825777769088745, 0.2161228507757187, 0.23026490211486816, 0.33302512764930725, 0.17925702035427094, 0.23004259169101715, 0.21795198321342468, 0.25560909509658813, 0.27245813608169556, 0.3083501160144806, 0.15593039989471436, 0.2846328914165497, 0.23478209972381592, 0.21092940866947174, 0.23806338012218475, 0.19657306373119354, 0.19120842218399048, 0.23265302181243896, 0.19639849662780762, 0.21426017582416534, 0.19651789963245392, 0.15901173651218414, 0.2203061282634735, 0.19705240428447723, 0.21341495215892792, 0.2199835181236267, 0.252154678106308, 0.26358845829963684, 0.25613000988960266, 0.2451172173023224, 0.23451736569404602, 0.22766375541687012, 0.24225912988185883, 0.28403574228286743, 0.260649174451828, 0.20655032992362976, 0.2851592004299164, 0.20703887939453125, 0.2178533673286438, 0.22090493142604828, 0.2765570878982544, 0.21688978374004364, 0.2522929906845093, 0.19188566505908966, 0.2712284326553345, 0.28391215205192566, 0.23511266708374023, 0.21629303693771362, 0.2849838435649872, 0.21615473926067352, 0.29330557584762573, 0.30729788541793823, 0.29220643639564514, 0.23772971332073212, 0.24203209578990936, 0.1750449687242508, 0.20324267446994781, 0.1996951401233673, 0.2730804681777954, 0.2157219648361206, 0.18827582895755768, 0.22196650505065918, 0.3062785565853119, 0.25930705666542053, 0.2165362685918808, 0.2659350633621216, 0.2488391399383545, 0.1757514923810959, 0.2293841689825058, 0.22136668860912323, 0.20821340382099152, 0.24322374165058136, 0.257137656211853, 0.23179742693901062, 0.24431657791137695, 0.22730576992034912, 0.23328933119773865, 0.2553585469722748, 0.21275432407855988, 0.18179172277450562, 0.16552972793579102, 0.2503354549407959, 0.26754632592201233, 0.2187000811100006, 0.28402766585350037, 0.20683060586452484, 0.18806736171245575, 0.19811999797821045, 0.3213862478733063, 0.20998866856098175, 0.2751528322696686, 0.1948128491640091, 0.23329798877239227, 0.20776990056037903, 2.680905818939209, 1.7164232730865479, 2.6874914169311523, 1.9920014142990112, 2.161973237991333, 3.223747491836548, 2.5239274501800537, 2.0458922386169434, 2.7873318195343018, 2.3848814964294434, 2.321876287460327, 2.7367336750030518, 2.842238187789917, 3.4947350025177, 3.0734546184539795, 3.2849044799804688, 3.491650342941284, 2.986942768096924, 3.4656853675842285, 1.9994933605194092, 2.7790703773498535, 3.0307583808898926, 3.8502442836761475, 1.9685583114624023, 2.4628002643585205, 2.430323839187622, 3.122438907623291, 2.3910512924194336, 1.6401537656784058, 3.3597500324249268, 2.35927677154541, 3.2994472980499268, 2.0222082138061523, 3.405444860458374, 2.984687328338623, 2.348055601119995, 2.8568508625030518, 1.6952645778656006, 2.598381280899048, 2.572619676589966, 2.282379388809204, 2.752480983734131, 2.7975943088531494, 2.0795602798461914, 1.2072455883026123, 1.9941304922103882, 2.4922313690185547, 1.8505219221115112, 1.761431336402893, 2.8711764812469482, 3.5443694591522217, 2.1544525623321533, 3.4977211952209473, 2.677605152130127, 2.044705390930176, 2.077561378479004, 2.0723776817321777, 2.967123031616211, 2.934783935546875, 3.177690267562866, 2.273176908493042, 1.468996524810791, 2.690993547439575, 2.1275975704193115, 2.407099962234497, 2.707843542098999, 1.9463201761245728, 3.1754791736602783, 2.340550422668457, 1.9101969003677368, 2.7150521278381348, 2.594454288482666, 2.616499662399292, 1.7895216941833496, 2.4417941570281982, 2.4979822635650635, 1.6198577880859375, 1.8049814701080322, 2.37320613861084, 1.8461172580718994, 2.7175068855285645, 3.1639721393585205, 1.6742130517959595, 3.7384746074676514, 2.57537841796875, 3.197192430496216, 2.4254469871520996, 2.449363946914673, 4.798730850219727, 2.6769325733184814, 2.353739023208618, 2.9222970008850098, 1.7262276411056519, 2.6882286071777344, 3.906317949295044, 2.1642236709594727, 3.164217472076416, 3.8490917682647705, 2.8282089233398438, 4.884695529937744, 3.5538716316223145, 3.5908899307250977, 3.138367176055908, 3.0634384155273438, 2.2133395671844482, 1.8804409503936768, 3.122894287109375, 2.6790008544921875, 2.3365347385406494, 2.2591657638549805, 2.3186943531036377, 2.7407965660095215, 2.749695301055908, 2.8697216510772705, 3.6368541717529297, 2.0175068378448486, 2.720043182373047, 2.9305827617645264, 2.1771903038024902, 1.7966537475585938, 3.016069173812866, 2.8238329887390137, 3.092064380645752, 2.2177062034606934, 2.317437171936035, 1.7550737857818604, 2.573373317718506, 2.6070854663848877, 2.203732490539551, 2.5953402519226074, 2.662137985229492, 2.511624813079834, 2.591529369354248, 1.9058812856674194, 2.6843860149383545, 2.7388739585876465, 4.656977653503418, 2.9835896492004395, 3.356412887573242, 1.4937676191329956, 2.1298410892486572, 4.231611251831055, 2.62797474861145, 3.0485386848449707, 2.0413784980773926, 2.9862048625946045, 3.4900734424591064, 2.022252082824707, 2.785339832305908, 2.842205762863159, 3.1064789295196533, 3.224705219268799, 3.7989470958709717, 2.0309484004974365, 3.4527993202209473, 3.6502227783203125, 2.1209874153137207, 2.898571729660034, 2.585275173187256, 3.0604522228240967, 1.7910511493682861, 2.8248820304870605, 3.3992345333099365, 3.2252719402313232, 1.9818111658096313, 2.8906071186065674, 2.1167612075805664, 3.1265881061553955, 1.9348125457763672, 2.758016586303711, 2.678957462310791, 2.6803793907165527, 2.3313205242156982, 3.7313899993896484, 3.375107765197754, 2.907155990600586, 3.1827549934387207, 2.987091541290283, 2.6929779052734375, 3.2840240001678467, 2.872023820877075, 3.359246253967285, 3.0870678424835205, 2.9648430347442627, 1.9127018451690674, 2.4437577724456787, 4.12796688079834, 3.4609501361846924, 2.283431053161621, 2.3421521186828613, 1.9597219228744507, 2.7179722785949707, 2.510850667953491, 1.8270663022994995, 2.374067544937134, 2.8487868309020996, 1.6560397148132324, 2.511705160140991, 3.744234561920166, 1.807395339012146, 2.3207156658172607, 3.201829671859741, 2.5380563735961914, 2.0575506687164307, 1.9010465145111084, 2.809169292449951, 2.9558205604553223, 3.6748363971710205, 1.990334391593933, 3.8072783946990967, 2.1918764114379883, 1.880926489830017, 2.086197853088379, 2.74088978767395, 2.356537103652954, 2.6587846279144287, 2.59481143951416, 3.141512393951416, 1.8086076974868774, 2.2582907676696777, 3.4144482612609863, 2.338559627532959, 2.5517032146453857, 4.336689472198486, 1.9667463302612305, 2.0325560569763184, 3.3396270275115967, 2.065396308898926, 2.1967408657073975, 1.8081759214401245, 3.128357410430908, 2.451233148574829, 2.6042919158935547, 1.8944017887115479, 2.1765341758728027, 2.6194000244140625, 2.8551135063171387, 1.9139727354049683, 1.810961365699768, 2.9619572162628174, 3.024930953979492, 1.7463102340698242, 2.7671990394592285, 2.1237926483154297, 2.588240385055542, 3.344555377960205, 1.664847731590271, 2.2525124549865723, 3.4158520698547363, 3.419893741607666, 2.8844406604766846, 2.5867912769317627, 1.9082826375961304, 2.3825039863586426, 2.417351007461548, 2.5712714195251465, 2.693791151046753, 2.518301248550415, 2.098991632461548, 3.052837371826172, 3.1804890632629395, 3.2728264331817627, 2.6758522987365723, 3.579421281814575, 1.5031309127807617, 2.8330137729644775, 3.246311664581299, 2.125014543533325, 2.3055479526519775, 3.3107805252075195, 2.7579567432403564, 3.9144628047943115, 3.615328311920166, 3.0797295570373535, 3.236450672149658, 3.660381317138672, 2.1307079792022705, 2.283322334289551, 3.5030810832977295, 3.366030216217041, 2.280658721923828, 3.127101421356201, 3.1524791717529297, 2.6693522930145264, 2.1832845211029053, 2.3647735118865967, 3.287369966506958, 1.6901893615722656, 3.2587509155273438, 1.8726409673690796, 3.5621135234832764, 3.633873462677002, 2.1919538974761963, 3.7704343795776367, 3.9395077228546143, 2.2597496509552, 2.820781707763672, 2.1697182655334473, 1.956590175628662, 3.172407388687134, 192.5873565673828, 71.33132934570312, 293.0869140625, 200.133544921875, 161.302001953125, 361.9745178222656, 236.55487060546875, 152.6510772705078, 447.4601745605469, 146.35658264160156, 223.3159942626953, 93.49920654296875, 321.9873046875, 335.8203125, 168.52142333984375, 249.520263671875, 148.6258544921875, 93.0307388305664, 142.2033233642578, 365.3406677246094, 158.1529083251953, 424.0729064941406, 394.546630859375, 244.15440368652344, 361.99951171875, 47.958221435546875, 145.14776611328125, 225.24478149414062, 153.22442626953125, 212.83412170410156, 92.26616668701172, 564.3727416992188, 94.9794921875, 64.66522216796875, 55.087703704833984, 138.35891723632812, 93.29137420654297, 165.877197265625, 194.2274169921875, 411.4435729980469, 488.50054931640625, 218.5376739501953, 189.75624084472656, 231.82374572753906, 112.44075012207031, 186.0584716796875, 262.0535583496094, 150.347412109375, 159.705078125, 120.49320220947266, 254.877685546875, 173.5251007080078, 319.5917053222656, 368.6645202636719, 61.10638427734375, 193.9877471923828, 194.380859375, 208.33636474609375, 106.11479949951172, 74.66253662109375, 145.02294921875, 302.12353515625, 279.79840087890625, 323.32904052734375, 237.79124450683594, 183.59722900390625, 271.5606994628906, 53.20159912109375, 283.8788757324219, 114.89347076416016, 175.0364990234375, 354.01312255859375, 198.14889526367188, 176.8712921142578, 144.7008819580078, 156.00885009765625, 227.4910125732422, 138.4781494140625, 320.0950927734375, 379.9787292480469, 377.2013244628906, 93.5218505859375, 67.67596435546875, 269.2637939453125, 130.8328399658203, 81.51839447021484, 72.93763732910156, 181.7917938232422, 373.2301330566406, 208.1448974609375, 51.7905158996582, 81.09870147705078, 254.89761352539062, 238.84368896484375, 114.2734375, 76.01956176757812, 402.0965270996094, 110.15116882324219, 217.781005859375, 215.45745849609375, 480.9693603515625, 368.4146728515625, 86.37316131591797, 113.66268920898438, 182.4171905517578, 268.7257080078125, 114.67232513427734, 84.6658935546875, 90.40308380126953, 122.3948974609375, 261.4376220703125, 76.761474609375, 271.7215881347656, 125.2967529296875, 357.15924072265625, 56.33754348754883, 305.4886779785156, 119.72113037109375, 178.03428649902344, 130.5076904296875, 118.90185546875, 344.5021057128906, 345.49755859375, 422.014404296875, 120.645263671875, 155.8804473876953, 229.14085388183594, 68.9344482421875, 457.8129577636719, 70.701416015625, 46.66872787475586, 44.2833251953125, 323.3399658203125, 262.4686584472656, 112.5086898803711, 53.15603256225586, 63.519256591796875, 303.0157470703125, 303.8150329589844, 67.87835693359375, 193.5004119873047, 417.51397705078125, 140.2724151611328, 162.77542114257812, 178.0072784423828, 149.71859741210938, 174.4622802734375, 69.9345703125, 190.2846221923828, 94.27828216552734, 98.5115966796875, 130.47811889648438, 136.84674072265625, 194.51904296875, 286.12042236328125, 146.59576416015625, 287.69012451171875, 331.2596740722656, 288.345703125, 62.884647369384766, 254.97425842285156, 374.5990905761719, 289.7170104980469, 289.4891052246094, 51.5694580078125, 439.8431091308594, 560.3689575195312, 168.8844451904297, 112.1634521484375, 75.82378387451172, 324.0616149902344, 161.24853515625, 131.5096435546875, 242.39663696289062, 249.68077087402344, 43.675048828125, 311.4158935546875, 83.24327850341797, 349.63671875, 95.67010498046875, 97.05229949951172, 321.7750244140625, 91.48784637451172, 339.1938171386719, 100.89398193359375, 300.9084167480469, 471.4093322753906, 45.60133361816406, 132.1872100830078, 210.66709899902344, 104.42632293701172, 236.04144287109375, 420.9288635253906, 323.75933837890625, 101.96398162841797, 69.51453399658203, 235.9379425048828, 184.53530883789062, 235.20372009277344, 51.97306442260742, 281.4374084472656, 122.15848541259766, 314.02008056640625, 279.79931640625, 214.3309783935547, 406.13812255859375, 281.8914489746094, 110.83447265625, 263.605224609375, 344.0833435058594, 319.6286926269531, 181.22776794433594, 72.70477294921875, 218.9755401611328, 193.6800537109375, 62.570072174072266, 267.6246337890625, 51.93910598754883, 97.81328582763672, 406.6382751464844, 126.17813873291016, 266.2469787597656, 178.441162109375, 204.741943359375, 115.24028778076172, 195.878662109375, 176.73968505859375, 156.72634887695312, 340.03253173828125, 37.2867431640625, 79.47280883789062, 154.4347381591797, 301.64306640625, 112.85682678222656, 122.92147827148438, 54.67572021484375, 249.08311462402344, 117.22808074951172, 43.86768341064453, 189.08023071289062, 86.0047607421875, 281.4804382324219, 67.14714050292969, 79.22760772705078, 362.3411560058594, 88.01299285888672, 71.72039031982422, 226.3897247314453, 111.32352447509766, 88.12110900878906, 62.87396240234375, 46.9777717590332, 124.15766143798828, 47.242488861083984, 186.95062255859375, 54.751766204833984, 74.36153411865234, 108.34083557128906, 154.30638122558594, 38.94854736328125, 150.72987365722656, 285.2047119140625, 274.0165710449219, 165.5980224609375, 151.8712921142578, 234.62225341796875, 162.8725128173828, 98.2967529296875, 306.386474609375, 158.4613037109375, 312.2683410644531, 163.56524658203125, 291.1103820800781, 119.26134490966797, 182.96690368652344, 68.96449279785156, 203.533203125, 115.9984130859375, 276.4422912597656, 109.45985412597656, 115.4271240234375, 176.70166015625, 208.7976837158203, 344.4539794921875, 60.855194091796875, 326.42724609375, 156.128173828125, 277.97564697265625, 359.21929931640625, 104.16271209716797, 284.4325256347656, 168.11459350585938, 356.5238342285156, 124.39241790771484, 227.92919921875, 62.11519241333008, 219.30589294433594, 113.31749725341797, 93.16082763671875, 59.40583038330078, 1.585005760192871, 2.3099896907806396, 1.6310302019119263, 3.5602352619171143, 2.1424856185913086, 3.7759997844696045, 2.327169418334961, 2.845890998840332, 1.43578040599823, 2.854933977127075, 1.7238088846206665, 3.0179061889648438, 3.3904290199279785, 2.0779097080230713, 2.787559747695923, 1.901412010192871, 2.8539037704467773, 2.6165435314178467, 1.9623807668685913, 1.6374508142471313, 1.7142266035079956, 2.0956039428710938, 2.4113948345184326, 2.4368584156036377, 3.7645397186279297, 2.1098031997680664, 2.81740665435791, 1.106501579284668, 2.907059907913208, 2.028244972229004, 2.9665210247039795, 3.590784788131714, 2.903330087661743, 4.294233798980713, 2.7960331439971924, 2.828432559967041, 2.5661230087280273, 3.1737139225006104, 2.4115049839019775, 2.7959721088409424, 2.0128896236419678, 2.851128578186035, 2.2786500453948975, 2.809576988220215, 1.7314825057983398, 1.858590006828308, 3.0002124309539795, 2.4703457355499268, 2.978055715560913, 3.3613929748535156, 2.3260889053344727, 2.5629589557647705, 2.591059446334839, 1.7760734558105469, 1.7292366027832031, 3.0536413192749023, 2.168694019317627, 2.498574733734131, 2.707249641418457, 2.2992825508117676, 3.2485344409942627, 2.917689085006714, 2.9535861015319824, 1.3428051471710205, 3.5623912811279297, 2.369948625564575, 4.1486663818359375, 2.4775748252868652, 2.5482170581817627, 3.849250078201294, 1.7714852094650269, 2.71964168548584, 3.0580363273620605, 2.284295082092285, 1.0691277980804443, 1.5570555925369263, 2.298680305480957, 1.5192899703979492, 2.8508388996124268, 2.0925095081329346, 3.297672986984253, 2.3234364986419678, 2.0174572467803955, 2.539950132369995, 3.3160977363586426, 2.674689769744873, 2.7528765201568604, 2.94732403755188, 2.4280567169189453, 2.1899633407592773, 2.5200068950653076, 3.5929665565490723, 3.720332145690918, 2.1617631912231445, 3.7468059062957764, 3.3357036113739014, 3.0676090717315674, 2.3835909366607666, 3.2933740615844727, 2.7000949382781982, 2.5805087089538574, 3.7365505695343018, 3.8649206161499023, 3.1501705646514893, 2.8181161880493164, 2.6917858123779297, 2.2238783836364746, 1.705371379852295, 3.082078218460083, 2.7657666206359863, 2.435116767883301, 2.798013210296631, 3.2450671195983887, 2.691535234451294, 1.4199415445327759, 1.9482858180999756, 2.410083770751953, 2.1193454265594482, 3.7911503314971924, 1.9411420822143555, 3.2778453826904297, 1.8998746871948242, 2.1001367568969727, 2.3606033325195312, 1.2074799537658691, 2.2967331409454346, 3.4466216564178467, 3.00659441947937, 1.9006434679031372, 2.7011444568634033, 1.781779408454895, 2.264453411102295, 3.9120166301727295, 3.72086501121521, 2.2086212635040283, 3.1632471084594727, 2.225062370300293, 2.282031297683716, 2.835320472717285, 2.4664463996887207, 2.9390382766723633, 2.3955202102661133, 2.1422040462493896, 2.164677619934082, 1.8084207773208618, 3.3930504322052, 2.5037424564361572, 2.6179230213165283, 2.015399932861328, 3.2850780487060547, 1.661432147026062, 2.769366502761841, 2.0486059188842773, 1.1398935317993164, 2.204878807067871, 3.0257349014282227, 1.5656992197036743, 1.8530309200286865, 3.634280204772949, 2.6070995330810547, 3.064207077026367, 2.5097482204437256, 2.3926990032196045, 2.6547088623046875, 3.1326406002044678, 2.627703905105591, 2.0273261070251465, 1.7396726608276367, 2.517077922821045, 2.79032039642334, 3.044031858444214, 3.1871261596679688, 1.8337889909744263, 2.564969539642334, 2.7698583602905273, 1.4380619525909424, 3.434441566467285, 2.5755200386047363, 3.963751792907715, 2.5600426197052, 1.9979790449142456, 2.3162388801574707, 2.1886682510375977, 2.2604496479034424, 2.833674669265747, 2.360475778579712, 2.934434652328491, 2.0875866413116455, 2.6176979541778564, 3.731196880340576, 2.2359437942504883, 1.519315481185913, 2.977616548538208, 1.9877859354019165, 3.1878209114074707, 2.774611711502075, 2.509071111679077, 3.148350715637207, 2.0589184761047363, 2.459019660949707, 4.102693557739258, 1.88325035572052, 1.6777199506759644, 2.752171039581299, 3.168837785720825, 2.426945686340332, 2.4497718811035156, 3.0643951892852783, 1.7579553127288818, 1.9055265188217163, 3.6280713081359863, 2.988910436630249, 1.6496741771697998, 3.4185574054718018, 2.2373952865600586, 2.166598320007324, 2.74626088142395, 3.2149932384490967, 2.156895160675049, 2.267910957336426, 1.88054621219635, 2.1448450088500977, 1.9400200843811035, 3.1541337966918945, 2.809316396713257, 2.2362663745880127, 2.8950424194335938, 2.5847198963165283, 2.976057767868042, 3.1754982471466064, 2.9047627449035645, 3.1198463439941406, 2.222771644592285, 1.7263230085372925, 2.8149664402008057, 1.1325044631958008, 3.1221683025360107, 1.6031478643417358, 2.615231990814209, 3.1995325088500977, 2.7636983394622803, 1.4876259565353394, 4.0525689125061035, 1.3613287210464478, 3.428622245788574, 3.356297492980957, 1.975932240486145, 2.529423713684082, 3.2382304668426514, 2.2976930141448975, 1.9645400047302246, 3.6653928756713867, 2.9115288257598877, 2.1945319175720215, 2.4122438430786133, 2.3566389083862305, 2.6753337383270264, 2.8333559036254883, 2.785935640335083, 1.3764818906784058, 3.1802661418914795, 3.0036418437957764, 3.687331199645996, 3.5210728645324707, 4.0292863845825195, 2.3119823932647705, 2.3195486068725586, 2.0688273906707764, 3.1409008502960205, 2.1517932415008545, 3.552340507507324, 2.4093754291534424, 2.5352282524108887, 3.092832565307617, 2.5164995193481445, 3.1309521198272705, 1.6855477094650269, 2.8501806259155273, 3.3617656230926514, 2.082197427749634, 1.6936217546463013, 2.079716682434082, 2.9061291217803955, 3.7357704639434814, 2.517089366912842, 2.1794204711914062, 2.3730690479278564, 3.156494617462158, 1.1956571340560913, 3.2653913497924805, 2.722460985183716, 3.576134204864502, 2.835657835006714, 4.247992515563965, 4.1834330558776855, 2.895275831222534, 1.9175481796264648, 1.9424047470092773, 2.909360885620117, 2.976041078567505, 0.2615320384502411, 0.22130469977855682, 0.24909427762031555, 0.19700823724269867, 0.24921973049640656, 0.2307148277759552, 0.22959880530834198, 0.19696208834648132, 0.22220952808856964, 0.2409048229455948, 0.325269877910614, 0.2946341931819916, 0.26812756061553955, 0.19255873560905457, 0.2769324481487274, 0.2904152572154999, 0.23359015583992004, 0.17846710979938507, 0.24893733859062195, 0.22688372433185577, 0.222502663731575, 0.1950187385082245, 0.19256441295146942, 0.313252329826355, 0.3116980195045471, 0.1981843113899231, 0.2828690707683563, 0.16095267236232758, 0.2565624415874481, 0.21935735642910004, 0.2243005633354187, 0.19422705471515656, 0.2553000748157501, 0.18604326248168945, 0.2919890284538269, 0.2605137825012207, 0.26655706763267517, 0.1801355630159378, 0.22331702709197998, 0.28059062361717224, 0.24831923842430115, 0.2276555597782135, 0.2556261122226715, 0.1965397596359253, 0.17783324420452118, 0.14642876386642456, 0.2225569486618042, 0.2371894270181656, 0.23694464564323425, 0.3158370554447174, 0.22444605827331543, 0.24394424259662628, 0.2702730894088745, 0.2668191194534302, 0.23000338673591614, 0.23749682307243347, 0.2556687891483307, 0.17939741909503937, 0.1989557296037674, 0.18181194365024567, 0.33507147431373596, 0.2361644059419632, 0.21427954733371735, 0.26028719544410706, 0.25660404562950134, 0.24737611413002014, 0.2489069700241089, 0.269313246011734, 0.18653030693531036, 0.24792726337909698, 0.22951528429985046, 0.24643036723136902, 0.23053939640522003, 0.29179689288139343, 0.2505768835544586, 0.252737432718277, 0.24900396168231964, 0.19669580459594727, 0.22413107752799988, 0.24947427213191986, 0.23511119186878204, 0.15409089624881744, 0.2741272449493408, 0.20160451531410217, 0.19069699943065643, 0.19236598908901215, 0.2067839354276657, 0.23096637427806854, 0.33390378952026367, 0.3114418089389801, 0.21916858851909637, 0.24306944012641907, 0.227156862616539, 0.20854386687278748, 0.24907848238945007, 0.24737556278705597, 0.26608002185821533, 0.1834086924791336, 0.29461708664894104, 0.19978012144565582, 0.29985323548316956, 0.294798880815506, 0.2482779324054718, 0.32158681750297546, 0.27309149503707886, 0.31005653738975525, 0.27484285831451416, 0.2302907258272171, 0.2660523056983948, 0.22032175958156586, 0.25982290506362915, 0.20433638989925385, 0.26193472743034363, 0.27555930614471436, 0.2903081774711609, 0.24933375418186188, 0.21721427142620087, 0.26335379481315613, 0.21312853693962097, 0.19878387451171875, 0.22372977435588837, 0.2551518678665161, 0.24583253264427185, 0.23574620485305786, 0.22218230366706848, 0.2928544580936432, 0.277365118265152, 0.2463628351688385, 0.16877204179763794, 0.18220151960849762, 0.24339334666728973, 0.2542101740837097, 0.18936416506767273, 0.26527583599090576, 0.2521793246269226, 0.22461308538913727, 0.2197948396205902, 0.21663089096546173, 0.1806824803352356, 0.21704858541488647, 0.2259475588798523, 0.19048072397708893, 0.27435168623924255, 0.14586341381072998, 0.28219884634017944, 0.23606941103935242, 0.23978610336780548, 0.283447265625, 0.24495358765125275, 0.2821509838104248, 0.2005719691514969, 0.24245984852313995, 0.24458448588848114, 0.2232065200805664, 0.2190977782011032, 0.2125696837902069, 0.24688559770584106, 0.21442733705043793, 0.21615618467330933, 0.23628252744674683, 0.2067004293203354, 0.2662409245967865, 0.2943032383918762, 0.23681975901126862, 0.21478036046028137, 0.24325725436210632, 0.2035144567489624, 0.2845384478569031, 0.2429407835006714, 0.2856734097003937, 0.19323904812335968, 0.24723216891288757, 0.19012883305549622, 0.18846538662910461, 0.2357511669397354, 0.27421867847442627, 0.2767792046070099, 0.23075883090496063, 0.23913227021694183, 0.21520617604255676, 0.3254830837249756, 0.24993754923343658, 0.21211965382099152, 0.26412948966026306, 0.1890791654586792, 0.2726285755634308, 0.1890791803598404, 0.26510727405548096, 0.25995635986328125, 0.16475404798984528, 0.2476847767829895, 0.2648221552371979, 0.20036962628364563, 0.25024405121803284, 0.2417479306459427, 0.27395233511924744, 0.24438370764255524, 0.16763053834438324, 0.15953053534030914, 0.3099302649497986, 0.23116162419319153, 0.2454383820295334, 0.3085753321647644, 0.26430922746658325, 0.28053003549575806, 0.2961992621421814, 0.1999647170305252, 0.21929222345352173, 0.3093089461326599, 0.27222785353660583, 0.25626522302627563, 0.2598622441291809, 0.2896643877029419, 0.2677956223487854, 0.2603830397129059, 0.22891592979431152, 0.21991916000843048, 0.19245892763137817, 0.21369464695453644, 0.20838764309883118, 0.2945440113544464, 0.2073587030172348, 0.2168692946434021, 0.3046685755252838, 0.20731735229492188, 0.26332834362983704, 0.227695494890213, 0.2692277729511261, 0.2530374228954315, 0.21952567994594574, 0.21586351096630096, 0.20030958950519562, 0.2195248156785965, 0.33288246393203735, 0.18904538452625275, 0.18765966594219208, 0.21621467173099518, 0.18501880764961243, 0.1925382912158966, 0.1990671455860138, 0.2806661128997803, 0.18941207230091095, 0.2766306698322296, 0.20195205509662628, 0.22275535762310028, 0.23182423412799835, 0.21605172753334045, 0.21798263490200043, 0.2457677721977234, 0.2346479743719101, 0.240594744682312, 0.25369420647621155, 0.211445614695549, 0.22379598021507263, 0.2448478639125824, 0.21843385696411133, 0.20769836008548737, 0.194365993142128, 0.21679575741291046, 0.2765672504901886, 0.24921870231628418, 0.27945253252983093, 0.21776896715164185, 0.22984538972377777, 0.1941135674715042, 0.2865724563598633, 0.21931104362010956, 0.23720109462738037, 0.20062515139579773, 0.17296262085437775, 0.22061119973659515, 0.19020816683769226, 0.2611309289932251, 0.23836009204387665, 0.23032598197460175, 0.21247069537639618, 0.22363066673278809, 0.2259846031665802, 0.18225955963134766, 0.2067948877811432, 0.2663863003253937, 0.28558722138404846, 0.20038791000843048, 0.2763739824295044, 0.22789955139160156, 0.17626836895942688, 0.22823458909988403, 0.2697913646697998, 0.29053062200546265, 0.30194056034088135, 0.23190879821777344, 0.19330264627933502, 0.26952406764030457, 0.27337124943733215, 0.3200431764125824, 0.3169209063053131, 0.23427613079547882, 0.20071201026439667, 0.2099182903766632, 0.22049662470817566, 3.3127293586730957, 2.992753267288208, 3.377880096435547, 4.588342666625977, 1.3340612649917603, 2.682279586791992, 2.6566734313964844, 3.3388917446136475, 2.1272053718566895, 3.958207845687866, 2.451463222503662, 2.3692963123321533, 2.767906665802002, 2.5600943565368652, 4.6218085289001465, 2.459177255630493, 1.7132360935211182, 3.63555645942688, 3.302621364593506, 3.7124156951904297, 1.8744016885757446, 1.7460933923721313, 2.573828935623169, 1.9562482833862305, 2.5336105823516846, 2.814622163772583, 3.2531585693359375, 2.50852632522583, 1.7170586585998535, 2.8280398845672607, 2.0340445041656494, 2.681947946548462, 3.177931547164917, 3.514965772628784, 1.7313278913497925, 2.1579205989837646, 4.105793476104736, 1.9686565399169922, 3.8890621662139893, 3.5963635444641113, 3.116349935531616, 2.3338940143585205, 3.0357518196105957, 3.483903169631958, 2.180561065673828, 3.2909350395202637, 2.7258641719818115, 4.152027606964111, 1.8926408290863037, 3.432234525680542, 3.366164445877075, 2.5943939685821533, 1.788537859916687, 2.1412241458892822, 2.0677852630615234, 1.8660858869552612, 4.517803192138672, 1.8266830444335938, 3.19730544090271, 3.556880474090576, 1.6158032417297363, 2.6260323524475098, 2.4325804710388184, 2.408245086669922, 1.4144967794418335, 1.76824152469635, 4.050779342651367, 1.8013216257095337, 2.6867456436157227, 2.6733453273773193, 4.02362060546875, 2.6050610542297363, 3.017719030380249, 1.8395098447799683, 2.500596523284912, 2.8250763416290283, 3.729677677154541, 2.636119842529297, 1.7566879987716675, 3.7753701210021973, 3.430056571960449, 3.1792538166046143, 2.424464464187622, 2.1272664070129395, 1.8506433963775635, 2.692302703857422, 3.755833625793457, 2.8709781169891357, 2.2058191299438477, 2.1776785850524902, 2.743257999420166, 3.4186184406280518, 2.7837975025177, 1.992195725440979, 2.9929840564727783, 2.611112117767334, 1.5353050231933594, 2.281144857406616, 1.707171082496643, 1.6163222789764404, 3.8862991333007812, 2.094722032546997, 2.97119140625, 3.165750741958618, 1.5867067575454712, 1.967794418334961, 2.000356674194336, 2.511059522628784, 1.944100022315979, 2.0457558631896973, 3.2836079597473145, 2.895447254180908, 3.1150569915771484, 2.668394088745117, 2.9187042713165283, 2.2629804611206055, 2.7170803546905518, 2.6459503173828125, 2.0282633304595947, 1.7969415187835693, 3.2536799907684326, 3.0032756328582764, 2.1992287635803223, 3.503444194793701, 1.7073431015014648, 2.7238731384277344, 2.3174126148223877, 3.201937198638916, 2.5735015869140625, 2.1987380981445312, 3.112612247467041, 1.5851058959960938, 2.8730742931365967, 2.885071277618408, 2.0173914432525635, 2.713512420654297, 3.985901355743408, 2.1765146255493164, 1.8594125509262085, 2.2485673427581787, 3.242772340774536, 3.6978814601898193, 3.2357470989227295, 2.633596658706665, 2.1023378372192383, 2.293674945831299, 2.40210223197937, 2.9332878589630127, 3.8360838890075684, 2.0113372802734375, 3.1990301609039307, 3.5756664276123047, 2.760054349899292, 2.010617733001709, 2.5013394355773926, 3.2210023403167725, 2.487468719482422, 2.242830753326416, 2.5632035732269287, 2.033442735671997, 3.2444393634796143, 1.999463438987732, 3.4693615436553955, 3.1178863048553467, 1.9898693561553955, 3.237319231033325, 2.2482385635375977, 3.237736940383911, 3.4243550300598145, 3.478839635848999, 1.5650875568389893, 1.8886394500732422, 2.647486448287964, 2.361585855484009, 2.9479594230651855, 3.109666585922241, 2.6957345008850098, 2.459205150604248, 3.6282870769500732, 3.443614959716797, 2.4158263206481934, 2.5139617919921875, 3.1491458415985107, 2.9588189125061035, 2.304502248764038, 2.5156571865081787, 3.6046223640441895, 2.251707077026367, 1.8754754066467285, 2.6017842292785645, 1.9401640892028809, 2.1728262901306152, 1.7662652730941772, 1.9355831146240234, 3.1001458168029785, 3.2387688159942627, 2.541201591491699, 2.06126070022583, 2.010087490081787, 2.08097243309021, 2.0401527881622314, 4.704036712646484, 3.1537890434265137, 3.82299542427063, 1.9518675804138184, 3.9448254108428955, 2.742854356765747, 2.5064468383789062, 1.7335466146469116, 2.9726479053497314, 2.040585517883301, 2.073723316192627, 3.8853416442871094, 3.3254125118255615, 3.1838676929473877, 2.5374996662139893, 3.0132973194122314, 3.4813919067382812, 2.368892192840576, 2.3994174003601074, 2.4921016693115234, 2.0248947143554688, 2.8978869915008545, 2.1141915321350098, 2.9265377521514893, 2.8357925415039062, 2.4681649208068848, 2.5266528129577637, 3.2556657791137695, 2.265953302383423, 2.732025146484375, 1.9844965934753418, 2.6999270915985107, 3.1953189373016357, 3.3374087810516357, 2.3276991844177246, 2.9615395069122314, 3.2033092975616455, 1.848616600036621, 2.5692009925842285, 2.509052276611328, 4.077782154083252, 3.462588310241699, 2.2778923511505127, 2.3221805095672607, 3.1879677772521973, 3.689049005508423, 1.9819045066833496, 2.2345023155212402, 2.639302968978882, 2.7542202472686768, 3.1773316860198975, 3.1968493461608887, 2.789262056350708, 2.72007155418396, 1.5588396787643433, 3.255565643310547, 2.8909943103790283, 2.714043140411377, 2.939580202102661, 2.129608631134033, 2.178539276123047, 1.7380930185317993, 3.2472145557403564, 3.4078152179718018, 1.7343641519546509, 2.156266450881958, 2.9638423919677734, 3.4015934467315674, 2.070328712463379, 3.153308629989624, 2.4026427268981934, 3.4052891731262207, 3.141489267349243, 2.0065269470214844, 2.710197687149048, 2.7563273906707764, 1.9680761098861694, 1.8932366371154785, 1.8771101236343384, 2.2558975219726562, 3.2447662353515625, 2.9632790088653564, 2.6064977645874023, 3.2316734790802, 2.6554558277130127, 3.4705169200897217, 2.005864143371582, 1.854466199874878, 3.524888753890991, 2.210468053817749, 3.675626039505005, 3.3893237113952637, 2.8310039043426514, 3.509338855743408, 2.08378005027771, 4.2369208335876465, 3.3749711513519287, 3.3797008991241455, 3.183847188949585, 273.31158447265625, 269.87255859375, 239.02793884277344, 516.4609375, 69.2310791015625, 167.71556091308594, 358.10302734375, 73.59207153320312, 292.9861755371094, 117.8855209350586, 132.80352783203125, 104.3912582397461, 123.24417877197266, 174.65805053710938, 67.1045913696289, 359.9205627441406, 217.00938415527344, 300.1435241699219, 199.7549591064453, 680.1806030273438, 266.4062194824219, 170.1902313232422, 181.0218505859375, 278.95526123046875, 447.4307861328125, 140.335693359375, 377.5525207519531, 195.4346466064453, 114.56910705566406, 148.52667236328125, 298.4643249511719, 414.71685791015625, 150.1917724609375, 380.120849609375, 97.56927490234375, 132.99278259277344, 133.57383728027344, 139.67491149902344, 202.7384796142578, 65.45208740234375, 291.5207214355469, 76.319091796875, 221.7840118408203, 264.95709228515625, 222.89776611328125, 306.7266845703125, 113.72661590576172, 433.5475769042969, 289.92218017578125, 403.189453125, 153.25473022460938, 214.05918884277344, 42.08416748046875, 308.89501953125, 179.224609375, 309.7268371582031, 169.5762481689453, 289.2040100097656, 169.6071014404297, 140.96063232421875, 150.61810302734375, 357.99951171875, 161.91192626953125, 189.6307373046875, 64.48438262939453, 124.08821868896484, 54.217041015625, 183.42396545410156, 74.1602783203125, 291.5870361328125, 137.2409210205078, 233.3734893798828, 156.7822265625, 102.92778778076172, 212.13877868652344, 152.51898193359375, 237.0823974609375, 148.39476013183594, 96.7515640258789, 334.0252380371094, 139.0422821044922, 256.002685546875, 169.20152282714844, 104.05577850341797, 158.86355590820312, 274.3402099609375, 96.5921859741211, 278.2733154296875, 287.4050598144531, 54.48500061035156, 178.007568359375, 466.04248046875, 107.6766357421875, 423.1730041503906, 222.659912109375, 309.17999267578125, 36.3288688659668, 290.6896667480469, 243.1918487548828, 525.3008422851562, 182.08656311035156, 201.0659942626953, 205.9433135986328, 159.39144897460938, 195.39642333984375, 375.9797058105469, 392.260498046875, 315.68182373046875, 225.4820098876953, 445.36968994140625, 126.9914779663086, 73.60230255126953, 69.71484375, 47.23582077026367, 86.41232299804688, 146.7932891845703, 258.9443664550781, 83.013671875, 103.77007293701172, 193.451171875, 138.4559326171875, 83.55133819580078, 271.3337707519531, 71.03593444824219, 439.9325256347656, 174.74691772460938, 101.04471588134766, 165.884033203125, 163.20773315429688, 297.51702880859375, 42.035404205322266, 60.82586669921875, 93.98979949951172, 185.16921997070312, 687.6527709960938, 67.96307373046875, 551.5169677734375, 312.51898193359375, 228.17022705078125, 99.07806396484375, 78.11883544921875, 104.3963623046875, 456.17333984375, 66.23030853271484, 117.76234436035156, 144.80816650390625, 200.6141357421875, 400.0765686035156, 170.8173370361328, 114.95623016357422, 171.73733520507812, 185.509521484375, 77.84716796875, 248.96676635742188, 254.8987579345703, 194.88427734375, 69.35101318359375, 237.54052734375, 83.05757904052734, 367.8006286621094, 65.88164520263672, 135.67958068847656, 374.0649108886719, 251.38821411132812, 115.44007873535156, 99.2274169921875, 392.3793640136719, 250.8594512939453, 145.9122314453125, 116.0716552734375, 189.3230438232422, 222.26475524902344, 379.1307067871094, 167.37014770507812, 386.73345947265625, 166.77963256835938, 259.5861511230469, 132.2626953125, 175.3914794921875, 187.19363403320312, 153.39056396484375, 164.5643768310547, 442.5849609375, 120.80962371826172, 264.2252197265625, 89.95304107666016, 155.67755126953125, 137.3437042236328, 138.08099365234375, 131.65618896484375, 338.3634948730469, 362.0968322753906, 219.6977081298828, 205.1546173095703, 105.43904113769531, 168.46176147460938, 337.12060546875, 225.3227081298828, 88.4580078125, 204.8271484375, 160.8139190673828, 129.9915771484375, 306.8800048828125, 206.1796875, 246.11875915527344, 164.9392547607422, 351.34625244140625, 352.3441467285156, 94.49610900878906, 88.44970703125, 188.0350341796875, 84.822265625, 171.2098388671875, 49.85805130004883, 139.89891052246094, 100.58709716796875, 48.280818939208984, 134.4423065185547, 211.5384979248047, 389.5981140136719, 74.8481216430664, 201.42727661132812, 237.9906005859375, 202.900390625, 245.900146484375, 348.7257995605469, 353.3246765136719, 199.8454132080078, 395.1014099121094, 49.84490966796875, 242.09417724609375, 396.56396484375, 317.9375, 283.00103759765625, 263.39111328125, 282.8204345703125, 166.9382781982422, 120.686279296875, 467.0545959472656, 70.5829086303711, 320.2657470703125, 133.98544311523438, 69.9363021850586, 134.85556030273438, 569.689208984375, 58.2137451171875, 176.0429229736328, 107.49005889892578, 153.27960205078125, 429.171875, 67.8834228515625, 152.09144592285156, 52.465633392333984, 151.7194061279297, 273.5168151855469, 111.53054809570312, 104.48282623291016, 113.26507568359375, 178.8485107421875, 301.02789306640625, 199.5323028564453, 218.07269287109375, 145.04443359375, 122.96202850341797, 228.26329040527344, 48.74859619140625, 165.935302734375, 332.4524841308594, 274.1792297363281, 51.75977325439453, 72.98346710205078, 305.64501953125, 340.8586730957031, 222.9595489501953, 224.39208984375, 73.88043975830078, 123.86583709716797, 93.8154296875, 59.214168548583984, 245.63548278808594, 246.25352478027344, 291.0259094238281, 96.8932876586914, 209.18960571289062, 61.96786880493164, 60.67165756225586, 133.865234375, 154.26377868652344, 434.8656005859375, 49.82080078125, 220.82980346679688, 104.25908660888672, 106.34110260009766, 91.42091369628906, 133.3286895751953, 207.8793182373047, 76.2193374633789, 68.69124603271484, 140.14540100097656, 249.8250274658203, 2.184664487838745, 3.4813671112060547, 3.15041446685791, 2.9163835048675537, 3.712254047393799, 3.564077138900757, 1.9704750776290894, 3.0820038318634033, 2.045212745666504, 2.4675521850585938, 3.004075288772583, 1.8161126375198364, 2.551699638366699, 1.7521694898605347, 2.8840878009796143, 1.8616704940795898, 3.219789981842041, 1.5461663007736206, 2.385693073272705, 3.6720287799835205, 3.826148509979248, 1.4232137203216553, 2.739367723464966, 2.707343101501465, 2.6658740043640137, 2.20815372467041, 2.1741690635681152, 2.900120258331299, 2.475414276123047, 2.1838650703430176, 2.68454647064209, 3.306098461151123, 3.023850679397583, 3.715224504470825, 3.6786699295043945, 2.144634246826172, 2.534184455871582, 2.74697208404541, 2.7511162757873535, 1.951996088027954, 2.2742414474487305, 2.660048246383667, 1.5428850650787354, 3.0671586990356445, 1.6463178396224976, 2.75777530670166, 2.3273608684539795, 2.01364803314209, 2.4621634483337402, 2.233205795288086, 2.075881004333496, 3.4843056201934814, 2.959120512008667, 1.791513204574585, 2.5310099124908447, 2.3115053176879883, 2.299808979034424, 2.8284802436828613, 3.655856132507324, 2.952014684677124, 3.286637544631958, 3.4541919231414795, 3.4953830242156982, 2.1291818618774414, 3.307398796081543, 1.6305227279663086, 2.318002462387085, 2.741999387741089, 3.101710557937622, 2.422929048538208, 2.4048779010772705, 2.14548397064209, 2.0052919387817383, 3.802006244659424, 1.9436239004135132, 1.6335828304290771, 2.1771650314331055, 1.9853259325027466, 1.9030230045318604, 2.2536990642547607, 2.1310601234436035, 3.6838958263397217, 1.6207131147384644, 3.1577465534210205, 2.5685436725616455, 1.7658051252365112, 2.974187135696411, 3.1160736083984375, 2.788378953933716, 2.6436550617218018, 2.7446365356445312, 2.9353129863739014, 1.809064269065857, 2.806920051574707, 3.9997851848602295, 2.541595458984375, 2.52790904045105, 2.6599762439727783, 1.6201810836791992, 3.313055992126465, 2.844656229019165, 1.8250112533569336, 1.5618836879730225, 3.4929518699645996, 2.53977632522583, 2.481828212738037, 3.4915521144866943, 3.1820902824401855, 3.0774319171905518, 2.174616813659668, 3.5890398025512695, 2.7000627517700195, 2.7562804222106934, 1.866835594177246, 3.0906896591186523, 2.951077699661255, 3.7520267963409424, 3.054736852645874, 3.053489923477173, 1.8485219478607178, 1.9656192064285278, 2.525650978088379, 4.154698848724365, 3.168402910232544, 2.222135066986084, 2.9244303703308105, 2.2800331115722656, 3.32096004486084, 2.0705020427703857, 3.232241630554199, 2.4795618057250977, 1.6628751754760742, 2.044793128967285, 2.5018723011016846, 3.704179048538208, 2.8314409255981445, 2.606398820877075, 3.501080274581909, 3.1128780841827393, 1.689617395401001, 1.9646825790405273, 3.929767370223999, 2.3394768238067627, 2.05267333984375, 2.792337656021118, 3.5492374897003174, 2.894726514816284, 2.064518928527832, 2.3599328994750977, 2.9206349849700928, 1.998976707458496, 2.0286684036254883, 2.2924611568450928, 2.771629810333252, 1.4619784355163574, 3.1186249256134033, 2.872807502746582, 2.0476465225219727, 2.3418262004852295, 2.6936700344085693, 1.492152214050293, 3.133620023727417, 2.414008140563965, 2.8243439197540283, 3.2259514331817627, 2.6485464572906494, 2.298611640930176, 1.77824866771698, 2.598407030105591, 2.2976152896881104, 2.7688512802124023, 3.7524688243865967, 3.1161835193634033, 2.522507667541504, 2.362133264541626, 2.4626717567443848, 4.0159711837768555, 1.7123616933822632, 3.3463985919952393, 2.4022793769836426, 2.502680778503418, 2.3759875297546387, 2.4600343704223633, 3.4111509323120117, 3.181056261062622, 1.7941374778747559, 3.49552059173584, 3.4660160541534424, 2.5406980514526367, 4.085822105407715, 3.2193119525909424, 2.526688575744629, 2.5966200828552246, 1.8151426315307617, 2.910693407058716, 2.160632848739624, 2.802210569381714, 4.26206636428833, 2.988135814666748, 1.977120280265808, 2.182023525238037, 2.8371715545654297, 2.07639217376709, 1.6794787645339966, 2.357131004333496, 2.300734519958496, 1.7457705736160278, 3.6514768600463867, 1.9855871200561523, 3.0183238983154297, 3.5102932453155518, 2.811481237411499, 3.0884692668914795, 2.1911497116088867, 2.00321888923645, 3.222968578338623, 3.016742467880249, 2.587212562561035, 2.8084325790405273, 1.661420226097107, 2.4485113620758057, 1.9300049543380737, 3.3620986938476562, 3.00028133392334, 1.8386754989624023, 1.6191598176956177, 2.5629796981811523, 2.0669164657592773, 3.014012336730957, 2.751497745513916, 3.7248411178588867, 2.836751699447632, 2.697718381881714, 2.115309715270996, 2.0939037799835205, 2.0986838340759277, 3.8226823806762695, 3.4532346725463867, 2.7163164615631104, 2.959214925765991, 2.016510248184204, 2.3933770656585693, 2.7148425579071045, 3.161498546600342, 3.1600353717803955, 2.692450523376465, 1.6327896118164062, 2.786099672317505, 3.873234748840332, 1.883785367012024, 2.2873315811157227, 2.25643253326416, 1.6013613939285278, 3.9926745891571045, 2.9514880180358887, 2.5803864002227783, 3.553422212600708, 2.698359966278076, 3.664628267288208, 3.5256035327911377, 2.2311203479766846, 2.2844324111938477, 3.0503687858581543, 2.479998826980591, 2.1611435413360596, 3.2288928031921387, 1.5095583200454712, 4.249260902404785, 1.515364646911621, 2.986628293991089, 3.2090237140655518, 2.7805633544921875, 4.105870723724365, 2.994884490966797, 3.787160634994507, 2.665538787841797, 3.346079111099243, 2.2229115962982178, 3.3850343227386475, 3.300464391708374, 2.1711721420288086, 2.6717793941497803, 2.03469181060791, 2.03855037689209, 2.5659782886505127, 1.5485591888427734, 3.371678352355957, 2.1553924083709717, 2.722827196121216, 3.50008487701416, 2.422891616821289, 2.9195175170898438, 2.7771687507629395, 2.823915958404541, 2.0329887866973877, 3.4646294116973877, 2.582033395767212, 1.8819018602371216, 4.093138217926025, 2.718116283416748, 0.21059410274028778, 0.24859637022018433, 0.1826101839542389, 0.3173922598361969, 0.22087901830673218, 0.2382560819387436, 0.20111684501171112, 0.16991378366947174, 0.2696997821331024, 0.23035922646522522, 0.17840518057346344, 0.19028085470199585, 0.25116732716560364, 0.2524135410785675, 0.18053320050239563, 0.27631914615631104, 0.24892334640026093, 0.22886674106121063, 0.20233558118343353, 0.2355441302061081, 0.3020547330379486, 0.2966911494731903, 0.22118814289569855, 0.25511065125465393, 0.2673715353012085, 0.23786936700344086, 0.21348348259925842, 0.2599146366119385, 0.2192797213792801, 0.25148847699165344, 0.20241513848304749, 0.24642221629619598, 0.17175711691379547, 0.2783616781234741, 0.30822694301605225, 0.2381947636604309, 0.2526056468486786, 0.2814426124095917, 0.19983628392219543, 0.2701592445373535, 0.18545889854431152, 0.2248305082321167, 0.19284245371818542, 0.24997787177562714, 0.2555500566959381, 0.2620214819908142, 0.25290828943252563, 0.26112064719200134, 0.2215205281972885, 0.26517096161842346, 0.18145179748535156, 0.230253666639328, 0.2526915371417999, 0.25245001912117004, 0.23620159924030304, 0.3009885251522064, 0.20723986625671387, 0.18606607615947723, 0.2875135540962219, 0.20492438971996307, 0.25766563415527344, 0.19868305325508118, 0.19264762103557587, 0.23104354739189148, 0.21084943413734436, 0.24233055114746094, 0.28141510486602783, 0.24766536056995392, 0.19154155254364014, 0.22553832828998566, 0.2658369243144989, 0.314594030380249, 0.20407474040985107, 0.19428375363349915, 0.27154341340065, 0.2129884511232376, 0.2796953320503235, 0.23277510702610016, 0.3099002242088318, 0.21449576318264008, 0.23449638485908508, 0.2568579912185669, 0.23689566552639008, 0.2521733045578003, 0.21993592381477356, 0.3189721703529358, 0.2666049599647522, 0.25528353452682495, 0.26062363386154175, 0.28935158252716064, 0.24539504945278168, 0.2632880210876465, 0.2275984138250351, 0.21061347424983978, 0.21256126463413239, 0.2057158350944519, 0.19058158993721008, 0.21473956108093262, 0.2726902663707733, 0.32251623272895813, 0.2988913655281067, 0.1971449851989746, 0.24115093052387238, 0.2240607589483261, 0.2809505760669708, 0.26781800389289856, 0.16813574731349945, 0.22382020950317383, 0.19726599752902985, 0.2576705813407898, 0.2525072395801544, 0.1928539276123047, 0.2360459417104721, 0.3168570399284363, 0.22988955676555634, 0.20255637168884277, 0.2959209978580475, 0.28030338883399963, 0.18215683102607727, 0.21576306223869324, 0.1733589470386505, 0.3385077118873596, 0.27191999554634094, 0.22068187594413757, 0.21967247128486633, 0.17959240078926086, 0.25235939025878906, 0.26919126510620117, 0.25995710492134094, 0.2603982090950012, 0.29355594515800476, 0.2331792414188385, 0.2650876045227051, 0.21068568527698517, 0.21941840648651123, 0.2069370001554489, 0.204707071185112, 0.24720466136932373, 0.18929000198841095, 0.20600144565105438, 0.21872305870056152, 0.23664413392543793, 0.2099025845527649, 0.2317904233932495, 0.2477215975522995, 0.28162285685539246, 0.2763519585132599, 0.22332167625427246, 0.28384989500045776, 0.16816648840904236, 0.2758879065513611, 0.2918850779533386, 0.3040708899497986, 0.2737891674041748, 0.2529311776161194, 0.2158702164888382, 0.24773941934108734, 0.22352969646453857, 0.283745676279068, 0.21147334575653076, 0.27221208810806274, 0.2257455587387085, 0.21335633099079132, 0.3073224127292633, 0.30118805170059204, 0.22498570382595062, 0.21796396374702454, 0.19900676608085632, 0.20475395023822784, 0.2576963007450104, 0.22987715899944305, 0.22738268971443176, 0.22282859683036804, 0.21153783798217773, 0.25933054089546204, 0.20362848043441772, 0.244949609041214, 0.26395687460899353, 0.2274267077445984, 0.2580036520957947, 0.2898207902908325, 0.263981431722641, 0.23466873168945312, 0.18730540573596954, 0.2260424792766571, 0.20925253629684448, 0.23212972283363342, 0.24463164806365967, 0.2933840751647949, 0.27148789167404175, 0.3104665279388428, 0.28015658259391785, 0.26313143968582153, 0.1430189311504364, 0.2935299277305603, 0.2549508213996887, 0.16608285903930664, 0.22619110345840454, 0.20939479768276215, 0.26609179377555847, 0.2695157825946808, 0.27004697918891907, 0.21772371232509613, 0.234260693192482, 0.26891475915908813, 0.21842524409294128, 0.2690458297729492, 0.26536762714385986, 0.2697756886482239, 0.2652930021286011, 0.23180145025253296, 0.2531859278678894, 0.338041752576828, 0.23878049850463867, 0.20729729533195496, 0.23468442261219025, 0.18231208622455597, 0.22486723959445953, 0.29735177755355835, 0.29833391308784485, 0.3520398736000061, 0.2594830393791199, 0.24197690188884735, 0.1710975170135498, 0.2322830855846405, 0.2140721082687378, 0.1770387589931488, 0.25419941544532776, 0.1805514544248581, 0.2017107754945755, 0.25339415669441223, 0.2700589895248413, 0.22519946098327637, 0.26245471835136414, 0.23844066262245178, 0.20967736840248108, 0.24946437776088715, 0.21073371171951294, 0.2616833746433258, 0.25257572531700134, 0.26399898529052734, 0.2237837165594101, 0.21837365627288818, 0.24723926186561584, 0.2206457108259201, 0.22128088772296906, 0.2601925730705261, 0.22077398002147675, 0.18205539882183075, 0.18290111422538757, 0.2782619893550873, 0.23911325633525848, 0.252028226852417, 0.24640636146068573, 0.2623059153556824, 0.20271100103855133, 0.17457734048366547, 0.16663210093975067, 0.2341659814119339, 0.2126072645187378, 0.14589282870292664, 0.20067816972732544, 0.2837218940258026, 0.22001630067825317, 0.3063102960586548, 0.26718151569366455, 0.2622320055961609, 0.286509245634079, 0.2774156332015991, 0.20587921142578125, 0.3116035461425781, 0.27461057901382446, 0.25001680850982666, 0.18876439332962036, 0.26910629868507385, 0.2031724750995636, 0.21451692283153534, 0.20851962268352509, 0.15561635792255402, 0.20664137601852417, 0.24571357667446136, 0.21347491443157196, 0.2174166887998581, 0.239170104265213, 0.22854425013065338, 0.22343619167804718, 0.23144415020942688, 0.2419072836637497, 0.19138386845588684, 0.19218935072422028, 0.2338763326406479, 0.24838674068450928, 0.2021634578704834, 0.2665826976299286, 0.25083041191101074, 0.28159335255622864, 0.27839741110801697, 0.2178572416305542, 0.2270243912935257, 0.18609049916267395, 2.5655126571655273, 2.3188791275024414, 3.2386162281036377, 2.9162628650665283, 2.643162250518799, 4.497688293457031, 1.9476286172866821, 2.8868229389190674, 3.1136085987091064, 2.7020175457000732, 2.1343955993652344, 3.1019222736358643, 2.107189655303955, 3.2496914863586426, 2.4875428676605225, 3.934756278991699, 2.6812102794647217, 2.5208401679992676, 1.8454560041427612, 3.2063229084014893, 3.834881544113159, 2.7100274562835693, 3.2699666023254395, 2.777789831161499, 4.030556678771973, 3.2104103565216064, 3.263334274291992, 2.134286642074585, 2.6993725299835205, 2.8925812244415283, 2.414384126663208, 2.3042988777160645, 1.7002859115600586, 2.5212416648864746, 3.2043514251708984, 2.4169459342956543, 2.663381338119507, 2.467723846435547, 2.2213258743286133, 2.251512050628662, 1.625815987586975, 1.9489067792892456, 3.44901442527771, 2.433396816253662, 3.9692792892456055, 2.495628833770752, 2.993295431137085, 1.5405832529067993, 1.7527823448181152, 1.8550665378570557, 2.1475906372070312, 2.4434664249420166, 3.67651104927063, 2.7029435634613037, 2.5749077796936035, 2.7303683757781982, 3.2563905715942383, 2.5475082397460938, 3.1256535053253174, 3.1295857429504395, 2.8009555339813232, 3.602304220199585, 3.2744698524475098, 2.409207344055176, 2.848247528076172, 2.2616841793060303, 1.8625472784042358, 2.305976629257202, 2.1634507179260254, 3.9012985229492188, 1.690813660621643, 4.2891316413879395, 2.772021532058716, 2.155911684036255, 3.459733247756958, 2.7204489707946777, 2.117323637008667, 2.5693047046661377, 2.5297746658325195, 2.263414144515991, 2.038400173187256, 2.034719467163086, 4.201932430267334, 4.216065883636475, 3.012895345687866, 2.936349630355835, 3.183537483215332, 2.7831501960754395, 2.7578811645507812, 3.374026298522949, 2.5068910121917725, 2.9014735221862793, 2.1891610622406006, 3.036628007888794, 2.204913377761841, 2.583810567855835, 2.5113368034362793, 2.8427257537841797, 3.6513450145721436, 4.217008113861084, 3.4885880947113037, 2.939549684524536, 2.630300760269165, 2.582631826400757, 2.9540672302246094, 2.7429604530334473, 2.081757068634033, 2.601823329925537, 3.620518207550049, 3.436795473098755, 2.8863513469696045, 3.1076738834381104, 2.4225573539733887, 2.3553543090820312, 2.9040558338165283, 2.5716464519500732, 2.766418933868408, 2.756145477294922, 2.121840476989746, 2.424471616744995, 3.0433006286621094, 2.1549081802368164, 2.504652738571167, 3.244093656539917, 1.757852554321289, 2.956230640411377, 3.5941874980926514, 2.4673619270324707, 3.0743789672851562, 2.5622310638427734, 4.062894821166992, 2.673642635345459, 1.8673231601715088, 3.8737761974334717, 2.2926056385040283, 2.0663022994995117, 2.703517436981201, 2.2049028873443604, 2.315955877304077, 2.2255566120147705, 4.31788969039917, 2.6979775428771973, 3.0694165229797363, 3.040727376937866, 3.630112886428833, 3.1425678730010986, 3.978131055831909, 3.2064530849456787, 2.326571226119995, 2.4017269611358643, 2.2513375282287598, 2.0324172973632812, 2.213608741760254, 3.8691024780273438, 3.6261818408966064, 3.0334866046905518, 2.1522176265716553, 4.080076694488525, 3.267409563064575, 3.090672016143799, 4.170614719390869, 2.580482006072998, 2.983293294906616, 3.2452752590179443, 3.1723058223724365, 1.9836196899414062, 1.9326788187026978, 2.502305030822754, 2.1488609313964844, 3.6650891304016113, 2.0891013145446777, 2.9071338176727295, 2.7411293983459473, 3.3126888275146484, 2.587275981903076, 2.5328478813171387, 2.016721487045288, 2.408949136734009, 2.4549756050109863, 3.0634865760803223, 3.140134811401367, 2.615919828414917, 1.5957767963409424, 3.8901302814483643, 1.986075758934021, 1.6154356002807617, 3.293951988220215, 1.9583992958068848, 2.4027819633483887, 2.4858174324035645, 2.0401501655578613, 2.67205810546875, 2.4189724922180176, 3.1059963703155518, 2.8206913471221924, 3.990267276763916, 1.6583222150802612, 2.203700542449951, 1.8470745086669922, 3.7272236347198486, 3.7065563201904297, 2.6036083698272705, 3.0716609954833984, 2.210523843765259, 3.438816547393799, 2.8856780529022217, 3.864100217819214, 2.630898952484131, 3.0875325202941895, 2.364755153656006, 2.6404693126678467, 3.264805316925049, 2.30224871635437, 1.9233306646347046, 2.6553726196289062, 2.790271043777466, 3.1798112392425537, 3.1704235076904297, 4.054634094238281, 2.232548713684082, 1.9407005310058594, 2.7353923320770264, 2.867995023727417, 2.186211585998535, 3.413149833679199, 3.3522109985351562, 1.5565605163574219, 1.9749491214752197, 2.5503785610198975, 2.735792875289917, 3.599412202835083, 3.8247146606445312, 2.056814193725586, 3.6056623458862305, 1.955597162246704, 2.5309572219848633, 2.624481201171875, 3.4619698524475098, 2.4550271034240723, 2.7701289653778076, 2.501220703125, 2.6402177810668945, 1.8024708032608032, 2.1769309043884277, 2.1895558834075928, 2.319079875946045, 2.9992434978485107, 2.291522979736328, 2.5755271911621094, 2.2384259700775146, 3.7574658393859863, 3.069592237472534, 2.8715972900390625, 2.4825167655944824, 2.621164083480835, 3.201390027999878, 3.1527562141418457, 4.276816368103027, 3.3750064373016357, 4.2975616455078125, 2.543285369873047, 2.708143949508667, 2.931096315383911, 2.8942947387695312, 2.0751864910125732, 2.527904748916626, 2.989049196243286, 4.111468315124512, 2.19887638092041, 4.68052339553833, 2.383396625518799, 3.0948245525360107, 3.839966297149658, 3.585637092590332, 3.0416786670684814, 1.797602653503418, 2.2011404037475586, 2.819797992706299, 3.229182243347168, 2.3392410278320312, 2.370859384536743, 2.1724886894226074, 2.2480452060699463, 2.878793954849243, 2.2051641941070557, 2.8483691215515137, 2.6494836807250977, 2.7358040809631348, 3.2492570877075195, 2.9356186389923096, 3.301645040512085, 2.874864339828491, 3.0761964321136475, 3.025611162185669, 2.2596280574798584, 2.733482837677002, 4.417741775512695, 2.56289005279541, 3.103386402130127, 2.059581756591797, 329.1458435058594, 602.1689453125, 457.3854064941406, 142.18231201171875, 306.32867431640625, 250.5043487548828, 141.3838653564453, 193.6164093017578, 358.0806884765625, 92.609375, 186.76934814453125, 241.2504119873047, 158.20709228515625, 259.40380859375, 157.64324951171875, 609.1663818359375, 44.984012603759766, 292.1519775390625, 236.34835815429688, 79.06732177734375, 130.469482421875, 253.922607421875, 120.67144012451172, 91.1436767578125, 83.49605560302734, 336.4063720703125, 115.88316345214844, 320.1794128417969, 128.135986328125, 364.4006042480469, 268.1514892578125, 81.77776336669922, 286.3421630859375, 64.7918701171875, 98.15008544921875, 293.6417236328125, 201.36178588867188, 360.0904541015625, 264.4404296875, 111.59720611572266, 78.48053741455078, 283.353515625, 347.4081115722656, 151.6999053955078, 203.0794677734375, 132.5556640625, 429.2278747558594, 123.36146545410156, 186.6458740234375, 68.06488800048828, 401.44873046875, 288.65533447265625, 74.8907470703125, 61.962772369384766, 239.5497589111328, 131.15585327148438, 207.07293701171875, 180.10302734375, 317.7906494140625, 53.24063491821289, 224.1687469482422, 322.6874084472656, 301.8656005859375, 485.7838134765625, 296.9474792480469, 242.0320587158203, 419.62603759765625, 133.91107177734375, 123.41913604736328, 256.48553466796875, 43.68122863769531, 220.70962524414062, 96.17886352539062, 454.90533447265625, 422.6275939941406, 316.80340576171875, 137.07943725585938, 111.63091278076172, 147.60963439941406, 95.20365142822266, 273.4956359863281, 114.89447021484375, 125.52632904052734, 369.1505432128906, 217.1045684814453, 47.245296478271484, 88.89904022216797, 313.5820617675781, 46.79518508911133, 172.36831665039062, 373.06085205078125, 279.82147216796875, 329.5011291503906, 128.80621337890625, 256.2279052734375, 466.425537109375, 139.7093505859375, 124.98693084716797, 162.79541015625, 182.96923828125, 188.1061553955078, 211.962890625, 300.4269714355469, 168.9953155517578, 153.14239501953125, 482.3037109375, 50.352783203125, 278.001708984375, 134.1415252685547, 147.5401611328125, 530.0629272460938, 204.0606231689453, 319.6380920410156, 222.2959747314453, 298.4699401855469, 315.76129150390625, 135.77447509765625, 193.942138671875, 64.66461181640625, 243.35516357421875, 238.11395263671875, 212.4008331298828, 155.17955017089844, 106.93177795410156, 300.697265625, 268.5110168457031, 189.0500030517578, 154.08935546875, 149.2620849609375, 146.5391387939453, 71.471923828125, 305.7977294921875, 424.2626037597656, 174.611572265625, 160.86380004882812, 134.2398223876953, 149.99046325683594, 159.166259765625, 65.86785888671875, 82.92860412597656, 215.6522216796875, 291.2645568847656, 90.6653823852539, 110.450439453125, 258.9544982910156, 172.00120544433594, 171.0455780029297, 347.56591796875, 195.93907165527344, 120.82427215576172, 252.66172790527344, 203.3900146484375, 263.99176025390625, 237.89208984375, 236.9124755859375, 265.681640625, 406.8097229003906, 218.90545654296875, 174.3946075439453, 113.03240966796875, 167.27989196777344, 54.82355880737305, 241.26235961914062, 210.7913818359375, 124.46112060546875, 366.147216796875, 196.72998046875, 182.03968811035156, 54.172420501708984, 125.17034912109375, 160.40089416503906, 131.06661987304688, 255.4486541748047, 157.04977416992188, 280.1798095703125, 161.7958221435547, 342.1625671386719, 165.1022186279297, 264.4285888671875, 139.47494506835938, 165.6522216796875, 176.7606964111328, 194.896484375, 85.59601593017578, 130.14866638183594, 499.735107421875, 214.15521240234375, 146.51173400878906, 405.7147216796875, 305.861328125, 78.7828369140625, 459.7457580566406, 60.86733627319336, 113.66228485107422, 391.74560546875, 119.7348403930664, 128.08311462402344, 202.1183624267578, 113.56771850585938, 146.3340301513672, 266.6999816894531, 112.97947692871094, 492.5865478515625, 278.9091491699219, 295.9886169433594, 391.9422912597656, 182.7928924560547, 185.9346466064453, 211.7183380126953, 197.0291290283203, 191.77066040039062, 118.00485229492188, 156.49142456054688, 131.56903076171875, 161.72335815429688, 222.1302947998047, 203.83056640625, 470.3460693359375, 87.66789245605469, 93.64991760253906, 87.6102294921875, 289.2589111328125, 414.6349792480469, 296.423828125, 438.32818603515625, 302.2889404296875, 186.73204040527344, 65.64893341064453, 398.9774475097656, 274.64520263671875, 143.6580047607422, 169.7295684814453, 284.7590026855469, 297.59722900390625, 297.198974609375, 137.6361083984375, 72.5618896484375, 210.81935119628906, 96.08689880371094, 458.7970886230469, 235.530517578125, 286.8885498046875, 114.49366760253906, 136.48582458496094, 293.4552001953125, 112.00882720947266, 122.071044921875, 192.1678009033203, 305.8341979980469, 233.6673583984375, 251.5155029296875, 125.45814514160156, 46.90656280517578, 394.4938049316406, 176.4610137939453, 215.1958770751953, 167.9865264892578, 148.88433837890625, 162.20985412597656, 146.4286651611328, 387.77734375, 229.1073760986328, 385.7945251464844, 472.544921875, 275.8962097167969, 163.06494140625, 448.3504943847656, 279.55035400390625, 117.34624481201172, 162.2152557373047, 73.0684814453125, 212.62664794921875, 211.0087890625, 320.02569580078125, 91.67300415039062, 151.9619140625, 216.51806640625, 226.26242065429688, 134.130126953125, 328.6332092285156, 162.95309448242188, 300.6327209472656, 140.9439697265625, 142.96705627441406, 63.4779052734375, 44.354061126708984, 215.6990966796875, 232.0906524658203, 174.3895721435547, 328.85601806640625, 131.04786682128906, 128.6237335205078, 141.92938232421875, 310.3503112792969, 133.6844482421875, 318.9880676269531, 267.1478576660156, 256.03033447265625, 50.383602142333984, 155.301025390625, 1.344199299812317, 2.599666118621826, 4.380061149597168, 2.951885938644409, 3.267117738723755, 1.930527925491333, 2.596287727355957, 3.605402946472168, 2.332974433898926, 3.3468172550201416, 3.1652779579162598, 1.9571377038955688, 1.6503231525421143, 2.2002508640289307, 2.383448839187622, 3.1240625381469727, 2.1060519218444824, 2.6798741817474365, 1.3194705247879028, 3.1761581897735596, 2.39359188079834, 2.373701333999634, 2.452216625213623, 1.526680588722229, 1.784035563468933, 2.3724796772003174, 2.9280920028686523, 1.854866623878479, 2.3526623249053955, 3.3839056491851807, 2.4560954570770264, 3.426608085632324, 2.8385651111602783, 2.175868034362793, 1.9843767881393433, 3.2785251140594482, 2.327615261077881, 3.198549747467041, 1.7745026350021362, 2.21225643157959, 3.9056901931762695, 3.258824348449707, 2.0738120079040527, 1.980266809463501, 4.262001991271973, 4.713122367858887, 2.2690343856811523, 2.061160087585449, 2.807943344116211, 2.0853092670440674, 2.9057705402374268, 2.4112348556518555, 2.379499673843384, 3.2199788093566895, 2.5413200855255127, 1.87239408493042, 2.154963493347168, 2.9669430255889893, 3.0867419242858887, 2.673692464828491, 1.7900818586349487, 2.7854394912719727, 2.0532236099243164, 3.3665478229522705, 3.7067253589630127, 2.187394142150879, 2.1214799880981445, 2.652256965637207, 2.692136764526367, 1.5822116136550903, 2.1357054710388184, 3.477280855178833, 2.735853910446167, 2.3551340103149414, 1.4828453063964844, 3.650954484939575, 3.104160785675049, 2.2195844650268555, 3.188865900039673, 2.4983463287353516, 2.1701161861419678, 2.4010379314422607, 2.0924606323242188, 3.2348413467407227, 3.092799425125122, 3.0996086597442627, 3.4927892684936523, 2.217738151550293, 2.5361032485961914, 2.517531633377075, 3.8749730587005615, 4.081794261932373, 2.9659318923950195, 1.2559728622436523, 2.9481918811798096, 1.4730024337768555, 2.791308641433716, 2.4615797996520996, 2.1975221633911133, 3.2027196884155273, 2.672882556915283, 2.096881866455078, 3.111884355545044, 1.9923561811447144, 2.134566307067871, 3.4910991191864014, 2.1826109886169434, 2.42655873298645, 2.4161462783813477, 2.4435510635375977, 2.5446882247924805, 2.8232128620147705, 3.6438493728637695, 3.2251555919647217, 3.653111457824707, 2.5200209617614746, 2.059683084487915, 2.5579710006713867, 1.3665215969085693, 2.281682014465332, 2.570276975631714, 1.891772747039795, 2.5170164108276367, 3.6180107593536377, 3.0597472190856934, 3.3720803260803223, 2.6722609996795654, 2.5478286743164062, 3.0383989810943604, 3.6939573287963867, 2.9855456352233887, 3.0363683700561523, 2.397655487060547, 1.717470407485962, 2.360957622528076, 3.3473904132843018, 2.5955777168273926, 2.9057092666625977, 1.6736654043197632, 2.0251874923706055, 2.0923547744750977, 3.5139782428741455, 2.1095974445343018, 2.783421754837036, 2.1231472492218018, 2.3427700996398926, 3.235232353210449, 2.70766544342041, 2.5576012134552, 1.9336504936218262, 3.627836227416992, 2.1045281887054443, 3.5988645553588867, 2.2189767360687256, 3.6270229816436768, 2.6916801929473877, 2.8623058795928955, 1.6820592880249023, 1.7024165391921997, 2.581251859664917, 3.7797701358795166, 2.676281690597534, 2.692997932434082, 1.8038631677627563, 2.454159736633301, 3.2800228595733643, 1.677016258239746, 2.8236303329467773, 2.761714220046997, 1.8803170919418335, 2.534693717956543, 2.6457812786102295, 2.757115364074707, 2.3743536472320557, 2.219204902648926, 2.3245270252227783, 2.1073999404907227, 2.3214218616485596, 2.0598714351654053, 4.191131591796875, 3.0355947017669678, 2.1842918395996094, 3.1322648525238037, 3.1250240802764893, 2.9541878700256348, 3.1372997760772705, 2.6059160232543945, 4.203864574432373, 2.3057756423950195, 2.0087335109710693, 2.882814884185791, 2.3537416458129883, 3.654543876647949, 1.827583909034729, 3.4878017902374268, 3.905613899230957, 1.4908264875411987, 2.176523447036743, 2.2704155445098877, 1.4618029594421387, 3.8308520317077637, 2.397778272628784, 3.179887533187866, 3.469244956970215, 2.165482521057129, 1.507197380065918, 2.435471773147583, 1.8010809421539307, 2.428154945373535, 1.6498746871948242, 2.4008047580718994, 2.387021064758301, 2.1719510555267334, 3.1829833984375, 2.025174140930176, 2.407806396484375, 2.545976161956787, 2.5497539043426514, 2.395207405090332, 1.570723533630371, 2.4482038021087646, 2.3990392684936523, 3.3830406665802, 1.6745671033859253, 3.154616594314575, 2.5639379024505615, 2.7212250232696533, 2.048781633377075, 1.6694658994674683, 2.4109270572662354, 2.0989346504211426, 2.1620960235595703, 2.024095058441162, 3.3874003887176514, 4.251972675323486, 1.485188364982605, 2.707892417907715, 2.317333221435547, 2.373419761657715, 2.329949378967285, 2.091372489929199, 2.45141863822937, 2.0999813079833984, 2.6231753826141357, 3.7024571895599365, 1.8858938217163086, 3.06339955329895, 2.94948673248291, 1.241017460823059, 3.1028664112091064, 3.6950795650482178, 1.9320687055587769, 2.4837024211883545, 2.513475179672241, 2.469614267349243, 1.9024056196212769, 2.3364808559417725, 2.62448787689209, 1.9106371402740479, 3.2144880294799805, 3.4520344734191895, 1.9042000770568848, 2.9113926887512207, 1.784730076789856, 2.1778993606567383, 2.0357916355133057, 3.582273483276367, 2.068596839904785, 2.6976959705352783, 3.4813737869262695, 2.4751222133636475, 2.032227039337158, 2.3388185501098633, 2.7495663166046143, 2.3457231521606445, 2.4388861656188965, 3.6445553302764893, 3.149941921234131, 2.324662208557129, 2.679426908493042, 2.6147093772888184, 3.6716854572296143, 2.567675828933716, 2.0709280967712402, 2.4687340259552, 2.511241912841797, 2.52400803565979, 1.9883774518966675, 1.9777342081069946, 1.9171018600463867, 1.6087008714675903, 3.2779362201690674, 2.803178071975708, 2.9485936164855957, 2.226231336593628, 3.3067502975463867, 1.8712068796157837, 2.4119179248809814, 2.1608173847198486, 2.106031656265259, 0.23325051367282867, 0.17851252853870392, 0.2254602015018463, 0.28921881318092346, 0.28539520502090454, 0.2618556618690491, 0.22712908685207367, 0.26717203855514526, 0.24102526903152466, 0.23732535541057587, 0.24082444608211517, 0.23539626598358154, 0.20426957309246063, 0.23131820559501648, 0.15462909638881683, 0.2020154595375061, 0.25744032859802246, 0.24273808300495148, 0.2935698628425598, 0.26159191131591797, 0.2089957743883133, 0.2411683201789856, 0.1780381202697754, 0.1965159922838211, 0.2798791527748108, 0.2940947413444519, 0.24379493296146393, 0.22835774719715118, 0.27932754158973694, 0.20893977582454681, 0.25596883893013, 0.21570944786071777, 0.3018515408039093, 0.2239963859319687, 0.283491313457489, 0.25010764598846436, 0.2448788434267044, 0.18521296977996826, 0.2537839114665985, 0.20770572125911713, 0.20182958245277405, 0.23787863552570343, 0.33038970828056335, 0.18787387013435364, 0.3207913935184479, 0.3090069890022278, 0.19917848706245422, 0.2879894971847534, 0.21699616312980652, 0.25895535945892334, 0.26157519221305847, 0.23764972388744354, 0.256059467792511, 0.12924166023731232, 0.20932090282440186, 0.2559168040752411, 0.2373172640800476, 0.22899168729782104, 0.31288227438926697, 0.24337045848369598, 0.20891129970550537, 0.28905189037323, 0.2475225031375885, 0.2482011765241623, 0.23174473643302917, 0.2771008312702179, 0.15771108865737915, 0.17962951958179474, 0.21192987263202667, 0.2649387717247009, 0.21723277866840363, 0.22231276333332062, 0.22289718687534332, 0.29267680644989014, 0.24039851129055023, 0.20403450727462769, 0.2342851758003235, 0.23262248933315277, 0.3005869686603546, 0.2192905694246292, 0.19778268039226532, 0.20970787107944489, 0.28900575637817383, 0.20952242612838745, 0.25895488262176514, 0.3453446924686432, 0.28729620575904846, 0.16160689294338226, 0.2010624259710312, 0.28891870379447937, 0.27611520886421204, 0.23815925419330597, 0.21213717758655548, 0.24400588870048523, 0.21988479793071747, 0.2845345735549927, 0.28414106369018555, 0.2175835818052292, 0.2607523798942566, 0.20771729946136475, 0.19804565608501434, 0.2634831964969635, 0.19488374888896942, 0.21200019121170044, 0.250916451215744, 0.21323204040527344, 0.18683487176895142, 0.27248188853263855, 0.25120049715042114, 0.2331085205078125, 0.18418101966381073, 0.19715340435504913, 0.2690431475639343, 0.23333396017551422, 0.2611996531486511, 0.19555552303791046, 0.2033306211233139, 0.2569081485271454, 0.20603656768798828, 0.20968487858772278, 0.2031443864107132, 0.22489528357982635, 0.23000328242778778, 0.21300069987773895, 0.26036131381988525, 0.3191440999507904, 0.266487717628479, 0.17561602592468262, 0.26754066348075867, 0.2469245046377182, 0.20723257958889008, 0.15066398680210114, 0.23477952182292938, 0.2564767003059387, 0.23985551297664642, 0.1686357855796814, 0.18491244316101074, 0.22633691132068634, 0.23553164303302765, 0.27856191992759705, 0.25874239206314087, 0.22887340188026428, 0.23294033110141754, 0.22660118341445923, 0.2055673897266388, 0.25877323746681213, 0.20802684128284454, 0.30337104201316833, 0.1904924362897873, 0.2119806557893753, 0.2609618604183197, 0.20915323495864868, 0.23761998116970062, 0.22836321592330933, 0.26541373133659363, 0.23021596670150757, 0.1921508014202118, 0.23048675060272217, 0.23301894962787628, 0.1821223348379135, 0.2840636670589447, 0.25538814067840576, 0.29157981276512146, 0.20652277767658234, 0.28363215923309326, 0.2062762826681137, 0.2417917549610138, 0.1695643961429596, 0.24445398151874542, 0.23747970163822174, 0.2198220044374466, 0.2700345516204834, 0.25856104493141174, 0.2431555539369583, 0.267291784286499, 0.18377704918384552, 0.20994125306606293, 0.2559155523777008, 0.19529291987419128, 0.2422524243593216, 0.26721110939979553, 0.2103850096464157, 0.20692595839500427, 0.2646918296813965, 0.252461701631546, 0.1950247585773468, 0.2807377576828003, 0.30246052145957947, 0.1894628256559372, 0.29959896206855774, 0.21661943197250366, 0.2029906064271927, 0.2212119996547699, 0.18973782658576965, 0.20639507472515106, 0.2007620930671692, 0.2061777412891388, 0.2383713722229004, 0.23532378673553467, 0.28644102811813354, 0.2819427251815796, 0.2725796103477478, 0.17490066587924957, 0.222700297832489, 0.21721680462360382, 0.2655186355113983, 0.28476428985595703, 0.20065192878246307, 0.20602703094482422, 0.2166403979063034, 0.22072601318359375, 0.21264083683490753, 0.25438421964645386, 0.23347385227680206, 0.2946740686893463, 0.231724813580513, 0.23950183391571045, 0.23605959117412567, 0.20204047858715057, 0.24132853746414185, 0.23476378619670868, 0.18180786073207855, 0.1846880167722702, 0.2142147570848465, 0.20394763350486755, 0.2645787298679352, 0.2454092800617218, 0.25547707080841064, 0.16376066207885742, 0.1979498565196991, 0.2310287207365036, 0.238835409283638, 0.26009559631347656, 0.22495467960834503, 0.255658894777298, 0.2246507853269577, 0.28654125332832336, 0.27546805143356323, 0.22514136135578156, 0.21913686394691467, 0.2727014124393463, 0.1562531590461731, 0.18627583980560303, 0.20567145943641663, 0.29220888018608093, 0.24534621834754944, 0.27745938301086426, 0.22667436301708221, 0.21464912593364716, 0.22609618306159973, 0.2895554006099701, 0.20592212677001953, 0.20386573672294617, 0.22860999405384064, 0.15018247067928314, 0.27322885394096375, 0.2930879592895508, 0.25731319189071655, 0.2321854531764984, 0.2049461007118225, 0.2743414342403412, 0.25027307868003845, 0.19767749309539795, 0.25132185220718384, 0.19343143701553345, 0.24519218504428864, 0.2094273567199707, 0.23937635123729706, 0.25049152970314026, 0.22781096398830414, 0.2250537872314453, 0.21051138639450073, 0.22472868859767914, 0.21852441132068634, 0.22506475448608398, 0.24784430861473083, 0.2594175934791565, 0.2081775665283203, 0.18627925217151642, 0.24049599468708038, 0.20913420617580414, 0.2128085345029831, 0.19148753583431244, 0.19409731030464172, 0.2323562353849411, 0.22376063466072083, 0.15779906511306763, 0.24126410484313965, 0.24514827132225037, 0.28082653880119324, 0.22198985517024994, 0.18462610244750977, 0.26134154200553894, 0.25886473059654236, 0.2615261375904083, 0.22142070531845093, 0.25627073645591736, 0.19723564386367798, 0.2402970790863037, 0.2812964916229248, 2.6801304817199707, 3.445408344268799, 3.7780041694641113, 3.0290608406066895, 2.2703018188476562, 3.1711795330047607, 3.757855176925659, 3.0235378742218018, 3.016589403152466, 2.662473201751709, 2.657167911529541, 2.458223581314087, 3.481451988220215, 2.4445245265960693, 2.1537277698516846, 3.3507626056671143, 1.7834469079971313, 2.8632214069366455, 4.07362699508667, 3.0860626697540283, 2.7964000701904297, 3.112492799758911, 3.3688981533050537, 2.1430623531341553, 2.7449891567230225, 2.413762092590332, 4.26349401473999, 3.4316563606262207, 1.941295862197876, 2.8728771209716797, 2.4072041511535645, 3.634719133377075, 2.5853631496429443, 2.0971791744232178, 2.68393874168396, 4.0298566818237305, 3.025364875793457, 3.636212110519409, 3.4083964824676514, 3.698436737060547, 2.6460325717926025, 4.152015209197998, 2.5718791484832764, 3.0784199237823486, 2.03550386428833, 1.6645281314849854, 3.280336856842041, 2.093839645385742, 2.926426410675049, 2.89677357673645, 4.16256046295166, 2.8971168994903564, 2.499903678894043, 2.279350519180298, 3.376532793045044, 2.8795700073242188, 2.742509603500366, 2.32987642288208, 3.111544132232666, 1.6596368551254272, 2.660508394241333, 4.15690803527832, 3.026384115219116, 1.8723520040512085, 2.8897628784179688, 2.857880115509033, 2.834740161895752, 2.4132983684539795, 3.8857624530792236, 2.4452531337738037, 3.56229567527771, 1.9479496479034424, 4.093414306640625, 2.441149950027466, 1.4048995971679688, 2.936568021774292, 1.9429130554199219, 2.3562233448028564, 1.860429048538208, 2.5998387336730957, 2.857245683670044, 2.673095703125, 2.8524773120880127, 2.2746756076812744, 3.1952438354492188, 1.8527706861495972, 2.279390811920166, 1.8876501321792603, 2.2703824043273926, 3.2574965953826904, 2.0755395889282227, 2.8572564125061035, 2.2149434089660645, 3.6479084491729736, 2.4742469787597656, 2.1218671798706055, 2.881636381149292, 3.0869531631469727, 2.245388984680176, 2.6291868686676025, 3.1281356811523438, 2.8719117641448975, 2.944946765899658, 3.0911736488342285, 3.658421277999878, 2.591937780380249, 2.8881382942199707, 3.0934693813323975, 2.2254576683044434, 3.189815044403076, 2.3465828895568848, 2.519388437271118, 4.300382137298584, 3.2190046310424805, 4.6920270919799805, 2.114560604095459, 3.0641448497772217, 2.94909405708313, 3.1635987758636475, 3.8638458251953125, 1.805415153503418, 2.777733325958252, 2.9538328647613525, 2.6973159313201904, 3.77268385887146, 3.426159620285034, 2.68662166595459, 3.6462223529815674, 2.677703857421875, 3.1873581409454346, 2.185102701187134, 3.247342348098755, 2.1466550827026367, 3.8810875415802, 2.0694262981414795, 3.1225979328155518, 3.795135974884033, 2.1751222610473633, 2.520962715148926, 3.6374568939208984, 2.524134635925293, 1.8966175317764282, 3.2063183784484863, 3.193451404571533, 2.739849805831909, 3.3014912605285645, 2.158442258834839, 1.8607158660888672, 2.845998764038086, 3.1951961517333984, 2.99882435798645, 2.867457866668701, 3.1415393352508545, 2.5938808917999268, 2.394279956817627, 2.2670347690582275, 2.281623125076294, 3.3612828254699707, 3.195164203643799, 3.4286105632781982, 3.602858781814575, 3.145793914794922, 1.6372209787368774, 3.654461622238159, 3.707620859146118, 2.833153247833252, 2.293613910675049, 2.919811248779297, 3.6264750957489014, 1.9165579080581665, 3.126288414001465, 2.190464973449707, 4.512528419494629, 4.173783302307129, 2.45392107963562, 2.1046462059020996, 3.764416456222534, 3.8027279376983643, 2.353832721710205, 1.6262526512145996, 3.1812121868133545, 2.740433931350708, 3.114016056060791, 3.3012585639953613, 3.3907482624053955, 2.8735573291778564, 3.5053317546844482, 2.5177977085113525, 3.198207139968872, 2.3707847595214844, 4.72318696975708, 2.568052291870117, 1.972764253616333, 2.93253231048584, 3.6612236499786377, 3.712128162384033, 2.0087506771087646, 1.7395899295806885, 3.370570659637451, 1.9457670450210571, 2.6214659214019775, 1.7701271772384644, 3.2363171577453613, 1.9620933532714844, 3.6156005859375, 2.477646827697754, 2.794095277786255, 1.610290765762329, 2.6331748962402344, 2.9805309772491455, 2.014524221420288, 1.7782938480377197, 3.4061038494110107, 2.6766655445098877, 2.461679220199585, 3.082810640335083, 3.1158788204193115, 3.770578622817993, 3.197582960128784, 2.996443510055542, 4.041652202606201, 3.5761210918426514, 2.2303054332733154, 2.6464874744415283, 2.449563503265381, 3.989610433578491, 3.313267946243286, 1.871118426322937, 3.7308480739593506, 4.217897415161133, 3.087622880935669, 3.4574227333068848, 1.8490492105484009, 3.5905697345733643, 2.3889925479888916, 3.0238006114959717, 3.174328565597534, 3.7309985160827637, 1.784515380859375, 2.2384698390960693, 2.4200406074523926, 2.7899553775787354, 1.5947703123092651, 3.756850481033325, 3.4721169471740723, 1.90496826171875, 3.9829845428466797, 3.0384304523468018, 2.979909896850586, 2.411526679992676, 3.1929290294647217, 2.755855083465576, 2.4625184535980225, 2.620471239089966, 3.212366819381714, 2.8104476928710938, 3.8567779064178467, 3.429529905319214, 2.7446823120117188, 2.061307907104492, 2.265605926513672, 2.417369842529297, 2.1941452026367188, 2.0472218990325928, 2.331270933151245, 1.7710342407226562, 3.2056450843811035, 2.2573904991149902, 3.0079548358917236, 3.2202045917510986, 2.280860662460327, 2.2743048667907715, 4.079267501831055, 2.8985652923583984, 2.3909809589385986, 2.739269971847534, 2.607257843017578, 2.7045159339904785, 2.689603805541992, 3.568098783493042, 2.6671042442321777, 2.433133602142334, 2.584165573120117, 2.765592575073242, 3.5517735481262207, 1.8104113340377808, 1.9318838119506836, 1.8945744037628174, 3.7152843475341797, 2.7307422161102295, 3.0948169231414795, 2.3868820667266846, 3.163745164871216, 2.2343502044677734, 2.7259767055511475, 3.37429141998291, 2.9709465503692627, 3.6888809204101562, 2.627277135848999, 2.4940414428710938, 357.8240661621094, 107.55597686767578, 219.6190185546875, 364.3644714355469, 365.4976501464844, 107.21649169921875, 158.08673095703125, 116.4188232421875, 88.27941131591797, 450.731201171875, 59.5673828125, 159.58370971679688, 142.47450256347656, 89.31554412841797, 108.23460388183594, 147.60430908203125, 66.65371704101562, 337.8034973144531, 50.55262756347656, 117.09571838378906, 127.90203857421875, 254.3386993408203, 166.2351531982422, 466.2110900878906, 331.1878967285156, 109.67749786376953, 195.56906127929688, 287.95526123046875, 146.9871826171875, 97.18093872070312, 132.40350341796875, 225.5683135986328, 200.06863403320312, 190.3378448486328, 168.91319274902344, 239.1693878173828, 80.7654800415039, 173.17100524902344, 158.3134765625, 104.15266418457031, 248.02487182617188, 36.1409912109375, 218.10166931152344, 123.4305419921875, 273.5369567871094, 704.292236328125, 615.5618896484375, 46.2152099609375, 119.61714935302734, 435.278076171875, 146.05084228515625, 266.41461181640625, 142.61236572265625, 90.89662170410156, 139.30889892578125, 325.9468994140625, 46.1927490234375, 44.17671203613281, 300.55889892578125, 309.883544921875, 141.27598571777344, 187.17593383789062, 97.75955200195312, 288.8412780761719, 336.008544921875, 252.6546630859375, 371.504638671875, 138.76910400390625, 132.4686279296875, 163.76580810546875, 203.0168914794922, 197.40293884277344, 233.763427734375, 641.3380126953125, 188.50550842285156, 84.36474609375, 114.50711822509766, 174.33116149902344, 232.04852294921875, 44.8646240234375, 207.8445281982422, 362.1740417480469, 250.95077514648438, 162.276611328125, 361.4563903808594, 124.45079803466797, 96.91857147216797, 148.11456298828125, 195.17550659179688, 152.3769073486328, 156.65391540527344, 192.78253173828125, 524.8782958984375, 255.74554443359375, 119.57328033447266, 182.9705352783203, 126.60411834716797, 109.0926513671875, 149.01365661621094, 429.0677490234375, 349.5331115722656, 483.3031005859375, 92.37871551513672, 478.3807067871094, 64.31071472167969, 92.57817840576172, 220.77078247070312, 369.0148010253906, 413.583740234375, 71.56729125976562, 40.5924072265625, 264.4693908691406, 158.8793182373047, 101.4481430053711, 86.6419906616211, 168.98838806152344, 49.34934616088867, 202.6074981689453, 184.95120239257812, 208.2137908935547, 228.40640258789062, 194.8667755126953, 148.5150909423828, 178.2744903564453, 242.28575134277344, 375.730224609375, 149.87493896484375, 178.1338653564453, 324.89599609375, 197.78944396972656, 381.0688171386719, 515.3541870117188, 156.5199737548828, 420.9942932128906, 106.6668930053711, 142.71029663085938, 66.32266235351562, 276.6379089355469, 108.04851531982422, 272.55712890625, 168.7658233642578, 63.54622268676758, 124.468505859375, 156.8026885986328, 145.3371124267578, 240.55532836914062, 87.50714874267578, 116.89212799072266, 478.23919677734375, 150.2508087158203, 114.6603775024414, 238.9500732421875, 397.8898010253906, 492.6455078125, 431.8818359375, 262.55413818359375, 141.51690673828125, 346.205810546875, 314.2460021972656, 337.0885925292969, 420.4447021484375, 317.3707275390625, 88.82160186767578, 108.41515350341797, 73.419921875, 517.6845703125, 56.5860595703125, 170.48643493652344, 199.9038848876953, 196.9674835205078, 311.8996276855469, 110.50045013427734, 77.149658203125, 349.78814697265625, 72.89336395263672, 196.96983337402344, 45.6748046875, 279.8894958496094, 211.63124084472656, 351.3572998046875, 485.244140625, 128.3423614501953, 108.01838684082031, 274.513427734375, 171.31307983398438, 111.86339569091797, 216.03616333007812, 285.0881652832031, 338.1402282714844, 168.15182495117188, 233.5775146484375, 278.45953369140625, 161.51220703125, 425.0550537109375, 404.19049072265625, 137.15721130371094, 345.4730529785156, 121.30745697021484, 116.27171325683594, 103.58920288085938, 131.66905212402344, 205.8466339111328, 360.0694885253906, 59.43354415893555, 379.07843017578125, 195.57864379882812, 59.6573600769043, 87.64263153076172, 108.73388671875, 336.21246337890625, 144.144287109375, 159.20611572265625, 438.1942138671875, 120.26622772216797, 231.3427276611328, 70.05654907226562, 290.9964599609375, 185.181396484375, 114.536376953125, 169.4657745361328, 155.82342529296875, 98.54337310791016, 173.7578125, 70.58657836914062, 422.5860900878906, 245.1773223876953, 97.74652099609375, 50.352142333984375, 92.90032958984375, 470.339599609375, 193.83799743652344, 368.4361572265625, 399.8443603515625, 417.5294494628906, 65.40734100341797, 165.64566040039062, 216.4213409423828, 158.53158569335938, 174.9608154296875, 86.07119750976562, 194.3710479736328, 231.04124450683594, 282.83917236328125, 128.05438232421875, 156.29495239257812, 309.1373291015625, 157.9368438720703, 183.40733337402344, 322.0286560058594, 79.53496551513672, 129.50518798828125, 108.07594299316406, 66.01420593261719, 135.64540100097656, 344.8586120605469, 298.6688537597656, 188.2047882080078, 292.7076110839844, 154.3747100830078, 156.6400146484375, 324.6304931640625, 322.9871520996094, 56.255950927734375, 275.3980712890625, 345.9378967285156, 295.86553955078125, 336.52691650390625, 249.2303466796875, 309.02069091796875, 147.78271484375, 332.6945495605469, 208.3144073486328, 103.38599395751953, 147.14788818359375, 55.136531829833984, 145.8415069580078, 104.44674682617188, 96.85689544677734, 109.08214569091797, 168.82470703125, 249.41278076171875, 114.22476959228516, 147.6160888671875, 501.411865234375, 271.4658203125, 345.831787109375, 164.37620544433594, 56.12862014770508, 379.6925354003906, 378.5836486816406, 357.9356994628906, 156.80615234375, 361.779052734375, 150.0142364501953, 251.0828094482422, 69.66449737548828, 211.28330993652344, 98.3187255859375, 544.602294921875, 155.774169921875, 3.835761308670044, 3.0231664180755615, 3.68315052986145, 2.879246711730957, 1.3488091230392456, 1.3867566585540771, 1.4770944118499756, 2.6903510093688965, 2.692187547683716, 2.1578474044799805, 1.5785784721374512, 1.8981996774673462, 2.599005937576294, 4.191702365875244, 2.4665446281433105, 2.557908296585083, 2.1302034854888916, 2.7330737113952637, 3.293971538543701, 2.260359764099121, 2.5166332721710205, 4.3026556968688965, 1.8850358724594116, 3.5848782062530518, 2.258115768432617, 2.94698429107666, 2.2315075397491455, 3.2513363361358643, 2.9173998832702637, 2.7492289543151855, 2.682194709777832, 2.5651519298553467, 2.8069121837615967, 3.618659019470215, 2.466729164123535, 1.8576706647872925, 1.3318612575531006, 2.1583681106567383, 2.2460763454437256, 3.093724250793457, 3.2258522510528564, 3.8011960983276367, 2.5059216022491455, 1.8206185102462769, 2.844802141189575, 3.752309560775757, 3.2263576984405518, 1.3591527938842773, 1.790155291557312, 3.9295494556427, 3.1787426471710205, 1.8301217555999756, 2.5449745655059814, 3.593395948410034, 2.955388069152832, 3.056464195251465, 3.771714687347412, 1.939624309539795, 3.6801910400390625, 2.214716911315918, 3.194683074951172, 1.8572908639907837, 3.093045473098755, 2.7738499641418457, 2.3602466583251953, 2.5962600708007812, 2.543837308883667, 1.606148600578308, 2.289553642272949, 2.1438751220703125, 2.249758720397949, 3.409212589263916, 2.5157880783081055, 3.2349941730499268, 2.61801815032959, 2.143662452697754, 2.385788917541504, 3.252041816711426, 3.105670213699341, 2.4196617603302, 2.587944507598877, 4.015060901641846, 1.9461989402770996, 2.091357707977295, 2.0992953777313232, 1.9074853658676147, 3.0051944255828857, 1.4007787704467773, 2.3143723011016846, 3.7243669033050537, 3.1296093463897705, 2.2799201011657715, 3.200869083404541, 2.4815163612365723, 3.1151084899902344, 2.654698371887207, 3.3167498111724854, 2.490586519241333, 1.2398334741592407, 1.7357491254806519, 2.19779109954834, 2.2739667892456055, 2.11337947845459, 2.2609176635742188, 1.9346189498901367, 1.924275517463684, 2.586132764816284, 2.6424646377563477, 2.7824482917785645, 2.206134557723999, 3.1691253185272217, 3.034752368927002, 2.446049690246582, 1.9993005990982056, 2.4174108505249023, 2.422893524169922, 3.3751630783081055, 3.019641160964966, 2.598578453063965, 3.085249662399292, 3.7730724811553955, 2.8494255542755127, 1.781947135925293, 2.3689584732055664, 2.254267454147339, 3.6964738368988037, 1.7930229902267456, 3.176813840866089, 2.011462450027466, 3.375138521194458, 1.6949807405471802, 2.6615753173828125, 3.43326473236084, 2.438858985900879, 2.5413966178894043, 2.5278496742248535, 2.398495674133301, 3.9449965953826904, 2.9997570514678955, 2.1432485580444336, 1.5743263959884644, 3.0031213760375977, 3.2934117317199707, 3.6913769245147705, 2.181279182434082, 3.3266687393188477, 3.1498003005981445, 2.8695483207702637, 2.461487054824829, 2.0494298934936523, 1.9235482215881348, 2.34460186958313, 2.107175827026367, 2.1589064598083496, 1.4845058917999268, 3.6964569091796875, 4.083664894104004, 3.511854887008667, 1.81194269657135, 1.7300063371658325, 2.5999419689178467, 1.9928573369979858, 2.9776031970977783, 3.7556142807006836, 2.1186420917510986, 2.6008458137512207, 3.529627561569214, 3.0037450790405273, 1.7632609605789185, 3.086125373840332, 2.41536545753479, 3.589280366897583, 3.068629026412964, 2.3492345809936523, 2.2556543350219727, 2.1639890670776367, 3.466689109802246, 3.7038028240203857, 3.3280961513519287, 1.9795769453048706, 3.406113862991333, 3.9488651752471924, 1.8756989240646362, 3.367065906524658, 2.462327718734741, 2.4103329181671143, 1.9714657068252563, 2.3608813285827637, 2.720458984375, 3.6048028469085693, 2.25895357131958, 1.9138851165771484, 3.4749398231506348, 2.038313865661621, 3.637779951095581, 3.1344082355499268, 2.7589797973632812, 3.4472570419311523, 3.013477325439453, 2.273653984069824, 2.894415855407715, 2.6329240798950195, 2.9133336544036865, 1.7898015975952148, 2.7367072105407715, 2.3122262954711914, 2.4103176593780518, 2.5689971446990967, 3.6668384075164795, 3.651343584060669, 3.0644044876098633, 2.767568588256836, 1.2395849227905273, 1.8435271978378296, 2.2617406845092773, 1.1868364810943604, 3.264211893081665, 2.8027007579803467, 2.4418649673461914, 4.013033866882324, 2.822916269302368, 2.749298095703125, 2.324154853820801, 2.2807419300079346, 2.93314266204834, 2.3375296592712402, 3.080634117126465, 2.477051258087158, 2.4467363357543945, 1.919260859489441, 2.9525463581085205, 2.4846620559692383, 3.4645442962646484, 3.013751268386841, 2.623105525970459, 2.2589950561523438, 3.074000120162964, 2.3796472549438477, 1.7088041305541992, 2.9079105854034424, 1.6147011518478394, 3.427731513977051, 2.4672422409057617, 2.609198570251465, 2.4153337478637695, 3.665046215057373, 3.9799110889434814, 2.331552028656006, 1.8729413747787476, 3.0131542682647705, 2.7785980701446533, 2.5214297771453857, 2.007601261138916, 2.91873836517334, 3.2531938552856445, 3.592076301574707, 1.8708248138427734, 3.637570381164551, 1.588976502418518, 2.154240608215332, 2.50925612449646, 2.3752031326293945, 2.5763206481933594, 2.563849449157715, 2.927649736404419, 2.5040838718414307, 1.5135831832885742, 3.8995678424835205, 1.9242515563964844, 2.6961236000061035, 2.1176538467407227, 2.8458337783813477, 3.511336088180542, 3.721757173538208, 3.224696159362793, 1.8133518695831299, 2.7471823692321777, 1.5122137069702148, 3.165257453918457, 1.7933225631713867, 2.368497610092163, 3.7863340377807617, 3.7715365886688232, 2.0549020767211914, 2.498865842819214, 3.372494697570801, 2.7412734031677246, 3.0868008136749268, 2.6446588039398193, 2.9049644470214844, 3.4319372177124023, 1.7853609323501587, 3.3857390880584717, 3.041032552719116, 3.2290749549865723, 2.236475944519043, 2.3072564601898193, 3.4627010822296143, 3.1536552906036377, 2.2343358993530273, 0.19902372360229492, 0.2123928964138031, 0.24363934993743896, 0.18885353207588196, 0.2125004529953003, 0.15824998915195465, 0.22927641868591309, 0.20885661244392395, 0.21813435852527618, 0.2688128352165222, 0.2226388156414032, 0.2375021129846573, 0.30154767632484436, 0.24027660489082336, 0.2114066332578659, 0.17430831491947174, 0.1999133974313736, 0.25344738364219666, 0.26112914085388184, 0.25039106607437134, 0.2917945683002472, 0.24134749174118042, 0.18992979824543, 0.21481500566005707, 0.26131781935691833, 0.28136950731277466, 0.2734490633010864, 0.20661313831806183, 0.27710023522377014, 0.25705164670944214, 0.2481771856546402, 0.263591468334198, 0.22547858953475952, 0.24009118974208832, 0.23042696714401245, 0.2888384461402893, 0.18549299240112305, 0.18873558938503265, 0.26800960302352905, 0.26654452085494995, 0.25113314390182495, 0.23422545194625854, 0.2341376394033432, 0.2275957465171814, 0.20075273513793945, 0.18666918575763702, 0.16663867235183716, 0.2151295393705368, 0.18325446546077728, 0.21203769743442535, 0.24844050407409668, 0.2984094023704529, 0.23162992298603058, 0.24264881014823914, 0.26480913162231445, 0.17930243909358978, 0.24503585696220398, 0.1937665492296219, 0.1900310516357422, 0.24847085773944855, 0.2065957635641098, 0.2191033661365509, 0.19747447967529297, 0.17163753509521484, 0.2063339501619339, 0.2650575041770935, 0.20479066669940948, 0.2708224058151245, 0.23807202279567719, 0.3170119822025299, 0.22880074381828308, 0.23358328640460968, 0.22716239094734192, 0.28325602412223816, 0.19265712797641754, 0.324188768863678, 0.24808095395565033, 0.2721562087535858, 0.24590285122394562, 0.22662711143493652, 0.2839757800102234, 0.2825038433074951, 0.24157893657684326, 0.2900947332382202, 0.223164364695549, 0.17748016119003296, 0.2721206545829773, 0.2558285593986511, 0.29046618938446045, 0.23809008300304413, 0.2568475008010864, 0.20400476455688477, 0.19863614439964294, 0.26732784509658813, 0.3103626072406769, 0.27715057134628296, 0.257180392742157, 0.2297322154045105, 0.30179131031036377, 0.22160165011882782, 0.22587871551513672, 0.21869397163391113, 0.27523159980773926, 0.15681332349777222, 0.1746140569448471, 0.2462082803249359, 0.2998434007167816, 0.26425811648368835, 0.30047738552093506, 0.28655481338500977, 0.283339262008667, 0.2552877962589264, 0.19835937023162842, 0.2443273514509201, 0.2966510057449341, 0.24389676749706268, 0.2739560604095459, 0.24564769864082336, 0.2665580213069916, 0.2588401138782501, 0.16037718951702118, 0.1810290813446045, 0.19545984268188477, 0.2004665583372116, 0.22686496376991272, 0.1473800539970398, 0.2564123868942261, 0.2754041254520416, 0.18439649045467377, 0.30853599309921265, 0.28115060925483704, 0.2748643159866333, 0.22329910099506378, 0.2365674525499344, 0.25745466351509094, 0.2591451406478882, 0.2609096169471741, 0.30288153886795044, 0.26707789301872253, 0.23763106763362885, 0.2812451124191284, 0.262416273355484, 0.28246238827705383, 0.20845361053943634, 0.15441478788852692, 0.20205360651016235, 0.17743073403835297, 0.24323701858520508, 0.18635062873363495, 0.20778365433216095, 0.23330648243427277, 0.21824347972869873, 0.2518392503261566, 0.25981274247169495, 0.27401304244995117, 0.2021399587392807, 0.2184867411851883, 0.22301892936229706, 0.24044547975063324, 0.18664728105068207, 0.24894152581691742, 0.28698793053627014, 0.23094546794891357, 0.24379253387451172, 0.2590284049510956, 0.3235137164592743, 0.20918981730937958, 0.23745036125183105, 0.2298896312713623, 0.30890926718711853, 0.2655293643474579, 0.23744529485702515, 0.2077912837266922, 0.2626740336418152, 0.2874445915222168, 0.1690426468849182, 0.20913159847259521, 0.22345994412899017, 0.25713032484054565, 0.1907782256603241, 0.3068751096725464, 0.2343900203704834, 0.18433769047260284, 0.1790977120399475, 0.26374587416648865, 0.26447799801826477, 0.23258309066295624, 0.2667483389377594, 0.24652600288391113, 0.2708987295627594, 0.25482088327407837, 0.2591318190097809, 0.22471724450588226, 0.2227591723203659, 0.27307868003845215, 0.27435386180877686, 0.2467384785413742, 0.29673126339912415, 0.19041861593723297, 0.18472041189670563, 0.18361365795135498, 0.23556531965732574, 0.2307741343975067, 0.24370011687278748, 0.31143590807914734, 0.16788959503173828, 0.29490360617637634, 0.21863318979740143, 0.2702014148235321, 0.2805016338825226, 0.2467513233423233, 0.24765554070472717, 0.24936196208000183, 0.23592029511928558, 0.28197118639945984, 0.24958178400993347, 0.18778559565544128, 0.2017272561788559, 0.2548127770423889, 0.32306450605392456, 0.2538687586784363, 0.3206120729446411, 0.25826495885849, 0.21924035251140594, 0.29126179218292236, 0.2570200562477112, 0.22875840961933136, 0.20687907934188843, 0.23693694174289703, 0.21305693686008453, 0.2761426866054535, 0.2740233242511749, 0.26487308740615845, 0.24278949201107025, 0.269272118806839, 0.2624596655368805, 0.27049562335014343, 0.2890265882015228, 0.2156107872724533, 0.2662924528121948, 0.18241892755031586, 0.17697344720363617, 0.19941863417625427, 0.23649954795837402, 0.3188636302947998, 0.19817660748958588, 0.19014804065227509, 0.23846930265426636, 0.28547731041908264, 0.16774769127368927, 0.2733101546764374, 0.26083675026893616, 0.2317279577255249, 0.20568415522575378, 0.2026730477809906, 0.29355329275131226, 0.2709748446941376, 0.25760573148727417, 0.27571699023246765, 0.24251426756381989, 0.21999400854110718, 0.19832885265350342, 0.2359350472688675, 0.2059062272310257, 0.20102328062057495, 0.2011987268924713, 0.20890025794506073, 0.2107948213815689, 0.18801338970661163, 0.33134546875953674, 0.2203974425792694, 0.3037126362323761, 0.2391282171010971, 0.24640683829784393, 0.2568475902080536, 0.22810550034046173, 0.19052709639072418, 0.22647185623645782, 0.25993895530700684, 0.2921546697616577, 0.25214770436286926, 0.26417866349220276, 0.20056119561195374, 0.28340864181518555, 0.2160012423992157, 0.19802728295326233, 0.21515464782714844, 0.24861009418964386, 0.24774114787578583, 0.25480154156684875, 0.24064236879348755, 0.23856210708618164, 0.1900354027748108, 0.2782934010028839, 0.271761417388916, 0.23124469816684723, 0.2169535607099533, 0.18694272637367249, 0.24307294189929962, 0.21271327137947083, 3.1368396282196045, 2.4566948413848877, 2.5700347423553467, 2.699528694152832, 1.7015184164047241, 2.7193803787231445, 2.0639610290527344, 1.893784761428833, 2.597172260284424, 3.5960757732391357, 2.9657084941864014, 2.6602330207824707, 3.851414442062378, 1.6689187288284302, 2.6420886516571045, 2.1944916248321533, 1.9824517965316772, 3.148298978805542, 2.5560050010681152, 2.97489857673645, 3.288706064224243, 1.8679745197296143, 3.294584274291992, 2.376966714859009, 1.7431349754333496, 1.9222195148468018, 2.932905912399292, 3.395829439163208, 3.488316774368286, 2.7676048278808594, 2.8027889728546143, 3.629166841506958, 3.381695508956909, 2.6194658279418945, 2.9413254261016846, 3.2431252002716064, 1.4339758157730103, 2.8945508003234863, 2.181649684906006, 3.1254794597625732, 2.274113178253174, 3.093654155731201, 3.8412437438964844, 2.995497941970825, 2.0322976112365723, 4.215618133544922, 2.7874157428741455, 3.1447389125823975, 2.548896312713623, 2.3530354499816895, 3.449185609817505, 1.7059649229049683, 3.067305326461792, 2.526836395263672, 5.093493938446045, 4.05633544921875, 3.895362138748169, 2.551215648651123, 1.8412871360778809, 2.880786180496216, 1.9698175191879272, 2.9967148303985596, 4.05953311920166, 2.068521022796631, 2.7678616046905518, 2.6477997303009033, 2.867495059967041, 2.2686188220977783, 2.895752429962158, 1.8652288913726807, 3.1914138793945312, 3.8396105766296387, 3.489046573638916, 3.6236572265625, 3.3538918495178223, 3.07317852973938, 1.7514266967773438, 2.6831600666046143, 3.0717527866363525, 2.144313097000122, 2.3143367767333984, 2.8023979663848877, 2.329860210418701, 2.333618402481079, 3.107163667678833, 2.92594313621521, 3.8523194789886475, 3.552710771560669, 2.0856001377105713, 2.5069572925567627, 4.890976905822754, 3.0404021739959717, 1.9272676706314087, 2.7174479961395264, 4.536599159240723, 2.664591073989868, 2.973409652709961, 2.2588369846343994, 2.08736252784729, 2.516101837158203, 3.378262758255005, 3.880241632461548, 2.3884634971618652, 3.8638856410980225, 1.935715913772583, 2.042314291000366, 2.5389442443847656, 2.055182933807373, 2.4606828689575195, 3.2760860919952393, 2.9112682342529297, 2.427196979522705, 1.642325758934021, 2.7053821086883545, 2.773163318634033, 2.3283445835113525, 2.7517406940460205, 3.7752208709716797, 3.92228627204895, 3.1170437335968018, 2.8935177326202393, 3.234337329864502, 2.436546802520752, 3.9133236408233643, 3.2654500007629395, 3.2142133712768555, 2.2682974338531494, 2.9462108612060547, 1.9521496295928955, 3.080758810043335, 3.892897844314575, 3.0957717895507812, 2.3120808601379395, 2.957162380218506, 4.32448673248291, 2.8649303913116455, 2.0852127075195312, 2.7635586261749268, 2.4315245151519775, 2.4338455200195312, 2.6814064979553223, 3.7787632942199707, 3.9680657386779785, 1.5776687860488892, 2.3633415699005127, 3.096240758895874, 1.8283538818359375, 2.877545118331909, 2.6523823738098145, 3.189009428024292, 3.269904375076294, 2.8276093006134033, 2.1018295288085938, 3.193342924118042, 3.810777425765991, 4.288242816925049, 3.227051258087158, 3.360321521759033, 2.8272411823272705, 2.2509117126464844, 2.138749122619629, 2.9065752029418945, 3.869114637374878, 2.8901078701019287, 3.019362688064575, 2.116184711456299, 3.3707680702209473, 2.913409471511841, 2.4682939052581787, 2.5815505981445312, 2.4751968383789062, 2.848820686340332, 3.49718976020813, 2.6833629608154297, 2.2837069034576416, 4.206576347351074, 2.4496231079101562, 2.7261462211608887, 1.8075933456420898, 2.611645460128784, 3.666520357131958, 3.488528251647949, 3.289701461791992, 2.886949300765991, 2.2958931922912598, 3.027177572250366, 3.428581714630127, 3.3194797039031982, 3.269247055053711, 2.471172332763672, 2.5065884590148926, 1.96888267993927, 3.019794225692749, 2.701742172241211, 1.9950226545333862, 1.9613131284713745, 3.9970333576202393, 2.792480707168579, 2.9548895359039307, 1.893851637840271, 2.575883150100708, 2.923582077026367, 3.1346511840820312, 3.010932207107544, 3.436992645263672, 2.3545336723327637, 3.2386138439178467, 2.2798852920532227, 2.176084518432617, 2.7202556133270264, 2.4497060775756836, 3.0426292419433594, 2.3479554653167725, 3.362361431121826, 3.124762773513794, 1.9449095726013184, 3.0345077514648438, 2.541698932647705, 2.431913375854492, 2.321786403656006, 3.4696972370147705, 1.9658502340316772, 3.462902069091797, 2.025174379348755, 1.9936094284057617, 2.37624454498291, 2.2696831226348877, 3.9215691089630127, 3.1576390266418457, 4.169126510620117, 3.7000393867492676, 2.9632561206817627, 3.730119466781616, 2.599782943725586, 2.809222459793091, 2.487818956375122, 3.5048704147338867, 2.36664080619812, 3.3777072429656982, 2.4868645668029785, 2.4497694969177246, 2.3502886295318604, 2.252748966217041, 1.8280216455459595, 4.410445690155029, 3.824565887451172, 2.465327739715576, 2.6556499004364014, 2.927546262741089, 3.1886682510375977, 3.036620616912842, 2.9007225036621094, 4.073356628417969, 3.3893871307373047, 4.098806381225586, 2.8619606494903564, 2.8524608612060547, 3.6900322437286377, 1.9055448770523071, 3.8257038593292236, 3.925662040710449, 2.494349479675293, 3.056718587875366, 2.892744779586792, 2.766005277633667, 2.154863119125366, 3.5864696502685547, 4.304380893707275, 2.7367730140686035, 2.3244431018829346, 2.9290719032287598, 2.1622068881988525, 2.6340582370758057, 1.8690651655197144, 2.038332223892212, 2.4368581771850586, 3.959047794342041, 2.1244091987609863, 2.0130317211151123, 3.214597702026367, 2.6193602085113525, 2.075221300125122, 2.8746109008789062, 3.6927490234375, 2.1156084537506104, 4.1613850593566895, 1.2342519760131836, 1.9616646766662598, 3.006592035293579, 2.951866626739502, 2.830806255340576, 3.263261079788208, 1.723083734512329, 2.1443846225738525, 3.0937836170196533, 2.5062789916992188, 2.131744384765625, 4.742623329162598, 1.955666184425354, 2.49428391456604, 140.7469482421875, 294.84765625, 175.58786010742188, 88.6593246459961, 125.00175476074219, 256.7425537109375, 74.55402374267578, 52.08563995361328, 76.07666015625, 509.3285827636719, 434.9865417480469, 292.6395263671875, 232.19505310058594, 165.73785400390625, 497.1469421386719, 98.59777069091797, 379.50921630859375, 199.67393493652344, 159.77517700195312, 380.5873107910156, 383.5731506347656, 326.7547302246094, 91.989990234375, 127.61669921875, 139.25482177734375, 82.578125, 164.5382843017578, 170.22418212890625, 121.82682037353516, 102.14080810546875, 50.9052734375, 317.0296630859375, 158.29258728027344, 75.58514404296875, 58.4813232421875, 291.4477233886719, 308.0666809082031, 91.8554458618164, 208.8553466796875, 43.69677734375, 301.57281494140625, 175.05870056152344, 206.68663024902344, 188.2001953125, 109.512939453125, 182.9429473876953, 177.33120727539062, 55.5350341796875, 169.04808044433594, 190.25991821289062, 116.65311431884766, 72.55286407470703, 188.69456481933594, 209.7664031982422, 237.80198669433594, 183.9510040283203, 163.10858154296875, 132.4579620361328, 74.1314697265625, 339.6814880371094, 168.7630615234375, 219.5365447998047, 81.77240753173828, 438.7530822753906, 132.12649536132812, 451.122802734375, 263.3431701660156, 213.515380859375, 118.18956756591797, 232.91053771972656, 60.3656005859375, 258.6717834472656, 47.8148193359375, 274.40045166015625, 52.72998046875, 251.06895446777344, 448.5028381347656, 140.34698486328125, 268.37957763671875, 322.9523620605469, 47.02553939819336, 229.8543701171875, 332.4086608886719, 445.609375, 352.6412048339844, 473.2451171875, 107.59355926513672, 163.4541015625, 134.1868438720703, 270.1330261230469, 176.8609161376953, 63.922245025634766, 317.3397521972656, 418.2125549316406, 62.271366119384766, 463.4367370605469, 435.6195068359375, 425.2030029296875, 81.5164794921875, 167.41046142578125, 244.8007354736328, 193.8496856689453, 93.70252990722656, 184.7181396484375, 328.5367126464844, 403.41552734375, 51.89264678955078, 271.34088134765625, 241.7854461669922, 147.173095703125, 367.903076171875, 104.21294403076172, 257.5649108886719, 160.99256896972656, 270.53131103515625, 535.7862548828125, 408.3138732910156, 125.16481018066406, 333.02081298828125, 136.27728271484375, 116.4061279296875, 116.35704803466797, 293.1227111816406, 136.0900115966797, 425.8205261230469, 269.66644287109375, 339.19647216796875, 549.4747314453125, 43.8735237121582, 165.7199249267578, 59.11914825439453, 250.12921142578125, 192.29261779785156, 236.35476684570312, 137.43955993652344, 97.86673736572266, 333.4971008300781, 209.94073486328125, 402.3466796875, 301.0958251953125, 339.03765869140625, 65.0146255493164, 209.6845703125, 257.00653076171875, 124.84111785888672, 70.7259521484375, 694.9122314453125, 298.2578430175781, 279.8982849121094, 194.4294891357422, 147.1988983154297, 249.0126953125, 141.14271545410156, 84.4129867553711, 296.45269775390625, 190.6953125, 197.68386840820312, 87.9072265625, 45.38492202758789, 171.97573852539062, 230.20037841796875, 47.56390380859375, 192.8300018310547, 118.74072265625, 131.70709228515625, 309.84271240234375, 267.30975341796875, 318.92138671875, 396.1639709472656, 397.5469970703125, 312.0716247558594, 263.6712646484375, 53.925838470458984, 180.5777130126953, 343.9657287597656, 105.98846435546875, 154.48448181152344, 283.46417236328125, 182.62705993652344, 383.2498779296875, 187.7322998046875, 566.997314453125, 401.2716369628906, 187.1459503173828, 206.92498779296875, 487.8455505371094, 62.7496223449707, 347.0841979980469, 191.05674743652344, 156.38282775878906, 336.8912353515625, 199.25257873535156, 295.3201904296875, 184.1483154296875, 216.93682861328125, 335.16070556640625, 290.26495361328125, 413.4415588378906, 218.284912109375, 357.7784729003906, 289.6998291015625, 138.51187133789062, 125.81089782714844, 179.94883728027344, 103.23189544677734, 251.47569274902344, 224.929443359375, 167.83657836914062, 454.143310546875, 248.7275390625, 249.50897216796875, 258.95458984375, 167.77749633789062, 150.223388671875, 55.42108154296875, 109.37493896484375, 416.8566589355469, 383.2921447753906, 312.3509826660156, 178.461669921875, 534.1693115234375, 58.24609375, 126.82930755615234, 430.3914794921875, 84.4446792602539, 190.95140075683594, 498.97393798828125, 362.927734375, 235.64218139648438, 231.379638671875, 69.08040618896484, 185.7479705810547, 60.281005859375, 312.4070129394531, 170.3123016357422, 200.23448181152344, 241.0235137939453, 460.2727966308594, 195.10406494140625, 118.10478210449219, 179.2334747314453, 250.46804809570312, 314.2845764160156, 71.94835662841797, 82.2200927734375, 288.4736328125, 308.71185302734375, 105.31945037841797, 231.8916778564453, 517.376953125, 341.7681884765625, 332.5933532714844, 276.6641845703125, 374.8722229003906, 242.1444091796875, 328.9602966308594, 428.7042541503906, 245.2587890625, 318.88641357421875, 129.330078125, 123.87972259521484, 77.13288116455078, 175.9452362060547, 222.736083984375, 212.627685546875, 219.57444763183594, 110.3084716796875, 155.28524780273438, 441.44171142578125, 219.3993682861328, 184.27503967285156, 122.38136291503906, 361.6678771972656, 227.4735565185547, 180.04653930664062, 182.08740234375, 266.2030334472656, 164.8870849609375, 313.23193359375, 208.8529052734375, 174.45335388183594, 83.70985412597656, 237.6834259033203, 312.2666015625, 378.7127990722656, 256.21435546875, 236.9686737060547, 303.86273193359375, 546.917724609375, 138.35850524902344, 351.1778869628906, 83.13910675048828, 142.40994262695312, 245.47715759277344, 128.06568908691406, 154.5153045654297, 72.78201293945312, 475.6195983886719, 135.16668701171875, 198.13198852539062, 2.4056499004364014, 1.2606216669082642, 2.769953489303589, 2.165424346923828, 2.865108013153076, 2.2986900806427, 2.4792850017547607, 3.6627514362335205, 2.332486152648926, 4.034296989440918, 3.0217297077178955, 1.9307106733322144, 4.0013933181762695, 3.0226616859436035, 2.180811882019043, 1.888808250427246, 2.999037504196167, 2.6463356018066406, 3.0997860431671143, 1.7889984846115112, 2.5624136924743652, 1.9755468368530273, 2.844858407974243, 3.1871559619903564, 3.432908296585083, 2.0277414321899414, 1.9083987474441528, 2.6719982624053955, 1.6760549545288086, 2.189314842224121, 1.9320062398910522, 1.6823333501815796, 3.30248761177063, 3.5454037189483643, 3.1114492416381836, 1.9234801530838013, 2.895322799682617, 2.679755449295044, 1.8268250226974487, 1.88978111743927, 3.909235954284668, 3.609745979309082, 2.846970796585083, 2.3923330307006836, 2.2397470474243164, 3.829615354537964, 2.7593345642089844, 3.358448028564453, 3.0921618938446045, 2.8449108600616455, 3.4832077026367188, 3.3324766159057617, 2.0654709339141846, 1.4945783615112305, 2.4647703170776367, 2.310014486312866, 2.9170141220092773, 3.0175042152404785, 2.043063163757324, 2.3306570053100586, 3.3349180221557617, 3.1073014736175537, 1.638395071029663, 3.369006872177124, 1.5080920457839966, 2.785644769668579, 2.4186925888061523, 1.9443520307540894, 2.5870697498321533, 3.4046294689178467, 1.7991420030593872, 1.6469321250915527, 2.5797204971313477, 2.478358268737793, 3.3671751022338867, 1.7645928859710693, 2.622082471847534, 2.142228126525879, 2.3971221446990967, 2.310612678527832, 1.9188909530639648, 4.1883134841918945, 2.3676555156707764, 1.411820650100708, 3.128392219543457, 1.908205270767212, 3.6023364067077637, 3.3072385787963867, 3.1018078327178955, 2.006524085998535, 3.4935407638549805, 2.2585747241973877, 3.449272632598877, 1.7109545469284058, 2.39743709564209, 2.157485008239746, 2.065657377243042, 3.1814186573028564, 1.6837725639343262, 1.7413768768310547, 1.9247076511383057, 4.282357215881348, 2.0323646068573, 3.0534889698028564, 2.3837153911590576, 2.4236483573913574, 2.269597053527832, 4.239306926727295, 3.624927282333374, 1.8979030847549438, 2.0782060623168945, 3.0369229316711426, 2.670527696609497, 3.699692964553833, 2.656534433364868, 2.25766658782959, 1.8941035270690918, 2.7542810440063477, 1.8660638332366943, 1.9804316759109497, 2.422133207321167, 2.135453224182129, 2.222569704055786, 3.244023323059082, 2.591484308242798, 1.470424771308899, 3.3051600456237793, 3.700303316116333, 3.05570125579834, 2.7084405422210693, 2.717210054397583, 3.3313610553741455, 1.964173436164856, 2.5101404190063477, 2.4755337238311768, 2.72951602935791, 2.3099563121795654, 2.39957332611084, 3.0334079265594482, 2.0086755752563477, 2.042156219482422, 3.363676071166992, 2.9335262775421143, 1.904405117034912, 3.4075417518615723, 2.7466952800750732, 3.12188720703125, 2.936410665512085, 2.790087938308716, 3.0973079204559326, 2.412905693054199, 3.0168449878692627, 3.0813381671905518, 3.1556975841522217, 1.885135293006897, 1.2338998317718506, 3.0654690265655518, 3.6088640689849854, 2.6820154190063477, 2.2330923080444336, 2.889666795730591, 3.702183723449707, 2.6324799060821533, 3.335891008377075, 2.914013624191284, 2.2543935775756836, 2.139950752258301, 2.9832732677459717, 2.64145827293396, 3.0088517665863037, 1.9777268171310425, 2.8840038776397705, 2.011392831802368, 2.7942898273468018, 2.6136298179626465, 3.954083204269409, 2.3512415885925293, 2.23087215423584, 2.6805260181427, 3.485557794570923, 2.648552894592285, 3.123868942260742, 1.5716581344604492, 2.7678747177124023, 1.975386619567871, 3.107011556625366, 2.4315919876098633, 1.8741792440414429, 2.6040728092193604, 2.5575380325317383, 2.2674150466918945, 2.9914965629577637, 3.5247573852539062, 2.9377236366271973, 2.37823748588562, 2.3487465381622314, 2.560114622116089, 2.5296754837036133, 1.7385494709014893, 1.836720585823059, 3.8375401496887207, 3.600311756134033, 2.0841903686523438, 2.7260611057281494, 2.6257176399230957, 2.149834632873535, 3.230611801147461, 4.287684440612793, 1.727982759475708, 1.7463833093643188, 2.4570369720458984, 3.4542036056518555, 1.7533621788024902, 2.212980270385742, 3.3243608474731445, 1.7853851318359375, 3.289982795715332, 4.298763751983643, 3.925851345062256, 3.19024395942688, 3.2298502922058105, 1.5460805892944336, 3.263077974319458, 3.1486828327178955, 3.0226640701293945, 2.4131956100463867, 2.2617905139923096, 1.4727849960327148, 2.4357759952545166, 3.5701396465301514, 1.8481698036193848, 3.2790844440460205, 2.345815420150757, 1.980854868888855, 3.5037107467651367, 2.949488401412964, 2.739436626434326, 3.7402775287628174, 2.638134717941284, 1.9244096279144287, 2.3731889724731445, 2.3274991512298584, 3.605741262435913, 2.46488356590271, 2.9162402153015137, 1.7708922624588013, 2.464564085006714, 3.6628904342651367, 2.3062496185302734, 2.9655447006225586, 3.341264247894287, 2.2792184352874756, 2.7905349731445312, 3.9043567180633545, 2.6825573444366455, 2.233738899230957, 2.688887357711792, 3.1007912158966064, 3.308278799057007, 3.1405868530273438, 2.606544017791748, 3.1828720569610596, 1.7370134592056274, 3.07562518119812, 2.961991548538208, 3.3424291610717773, 3.605259895324707, 3.274662971496582, 2.701350688934326, 1.703932285308838, 2.873514413833618, 2.1006762981414795, 2.944758892059326, 3.5071194171905518, 2.7096667289733887, 4.127386093139648, 2.6611168384552, 2.690631151199341, 1.8428339958190918, 3.5814695358276367, 3.705712080001831, 2.0075769424438477, 2.8537399768829346, 3.540208578109741, 2.7587339878082275, 1.743493914604187, 3.2609355449676514, 2.1729729175567627, 3.6395444869995117, 1.712148666381836, 2.9883499145507812, 2.962522268295288, 3.2989964485168457, 2.8440792560577393, 2.6508095264434814, 2.7239742279052734, 1.628122091293335, 3.382638454437256, 2.4882540702819824, 2.4736223220825195, 0.18688884377479553, 0.2438126653432846, 0.2107904553413391, 0.2285774201154709, 0.2597320079803467, 0.18283697962760925, 0.2531699538230896, 0.2325526773929596, 0.27735674381256104, 0.2632542848587036, 0.2745510935783386, 0.23097482323646545, 0.22527053952217102, 0.22257167100906372, 0.32040518522262573, 0.20247814059257507, 0.22836101055145264, 0.19948101043701172, 0.3025691509246826, 0.2450229525566101, 0.2533167898654938, 0.1810598373413086, 0.18544051051139832, 0.2914269268512726, 0.3363496959209442, 0.20601139962673187, 0.22605106234550476, 0.27679941058158875, 0.288818895816803, 0.26542946696281433, 0.22224198281764984, 0.2552104592323303, 0.2788740396499634, 0.22535620629787445, 0.28398334980010986, 0.2650373876094818, 0.2660786509513855, 0.2151518166065216, 0.27081796526908875, 0.26859813928604126, 0.24490271508693695, 0.24137648940086365, 0.24623186886310577, 0.21782249212265015, 0.2128889262676239, 0.24866199493408203, 0.2781278192996979, 0.2798346281051636, 0.21111904084682465, 0.18273110687732697, 0.2594105005264282, 0.23247848451137543, 0.195794939994812, 0.231403648853302, 0.15672025084495544, 0.25579655170440674, 0.22116480767726898, 0.2586480975151062, 0.22509588301181793, 0.26218071579933167, 0.2367827147245407, 0.245863676071167, 0.2630908489227295, 0.2388411909341812, 0.2782720923423767, 0.2826441824436188, 0.20566099882125854, 0.2503257989883423, 0.27712076902389526, 0.22946666181087494, 0.1966518610715866, 0.24581706523895264, 0.19213493168354034, 0.24458275735378265, 0.2905639111995697, 0.25720956921577454, 0.25055038928985596, 0.2669903337955475, 0.20264118909835815, 0.2662968039512634, 0.28271809220314026, 0.19659633934497833, 0.21860921382904053, 0.23763799667358398, 0.3214133381843567, 0.3066987991333008, 0.24928103387355804, 0.26174676418304443, 0.1807713657617569, 0.1900089830160141, 0.24864237010478973, 0.3061200678348541, 0.23502697050571442, 0.22672288119792938, 0.16621915996074677, 0.17888303101062775, 0.27498945593833923, 0.2775873839855194, 0.22009603679180145, 0.30866485834121704, 0.23334069550037384, 0.20713911950588226, 0.2757103741168976, 0.29772892594337463, 0.1893041878938675, 0.23131006956100464, 0.18391962349414825, 0.33645400404930115, 0.2481890618801117, 0.27478811144828796, 0.23325717449188232, 0.22656767070293427, 0.19276376068592072, 0.25073230266571045, 0.25765296816825867, 0.3013572692871094, 0.19198375940322876, 0.22311122715473175, 0.17932884395122528, 0.29822826385498047, 0.2700910270214081, 0.23958437144756317, 0.2116585522890091, 0.195815771818161, 0.2866159677505493, 0.2671348452568054, 0.23588763177394867, 0.24780993163585663, 0.20553439855575562, 0.27577459812164307, 0.19847318530082703, 0.24134071171283722, 0.2195214480161667, 0.23418360948562622, 0.2275717854499817, 0.266814649105072, 0.2586212158203125, 0.26290926337242126, 0.26440370082855225, 0.2738480865955353, 0.28809553384780884, 0.23021544516086578, 0.33441492915153503, 0.22922919690608978, 0.2659081220626831, 0.24308960139751434, 0.2906036674976349, 0.23359110951423645, 0.2506742775440216, 0.2667864263057709, 0.23423202335834503, 0.17286813259124756, 0.1923547387123108, 0.22401629388332367, 0.21584895253181458, 0.23545289039611816, 0.20226342976093292, 0.22778169810771942, 0.2545057535171509, 0.2028510570526123, 0.24289868772029877, 0.20098288357257843, 0.2121412456035614, 0.22118480503559113, 0.24407348036766052, 0.2846795916557312, 0.2242737114429474, 0.21655873954296112, 0.2896275222301483, 0.2631775140762329, 0.23219282925128937, 0.28057563304901123, 0.3002576231956482, 0.32536402344703674, 0.23364707827568054, 0.20461490750312805, 0.300960898399353, 0.2397388368844986, 0.275433212518692, 0.26556047797203064, 0.28401193022727966, 0.21208874881267548, 0.24494527280330658, 0.23233066499233246, 0.21542468667030334, 0.2054404467344284, 0.29632240533828735, 0.26702308654785156, 0.2716672122478485, 0.20097559690475464, 0.20976969599723816, 0.2074277102947235, 0.2913662791252136, 0.2138477861881256, 0.20279714465141296, 0.24509774148464203, 0.2353622019290924, 0.23525984585285187, 0.244174525141716, 0.300559937953949, 0.20897750556468964, 0.24110980331897736, 0.2288382351398468, 0.21138963103294373, 0.27052757143974304, 0.16536906361579895, 0.20484218001365662, 0.194143608212471, 0.2281295359134674, 0.20594947040081024, 0.2120228111743927, 0.2513876259326935, 0.22678202390670776, 0.17711016535758972, 0.215417742729187, 0.2992174029350281, 0.2511829733848572, 0.2461274415254593, 0.17240604758262634, 0.24058623611927032, 0.2097756564617157, 0.27087920904159546, 0.23252230882644653, 0.1651785969734192, 0.25811901688575745, 0.23344048857688904, 0.2460176795721054, 0.2787035405635834, 0.2785836458206177, 0.22576270997524261, 0.20302574336528778, 0.26640719175338745, 0.13000260293483734, 0.22848623991012573, 0.2817901074886322, 0.26721659302711487, 0.2295374572277069, 0.2826347351074219, 0.2627275288105011, 0.2512567341327667, 0.3134217858314514, 0.20976389944553375, 0.2957221567630768, 0.2576705813407898, 0.19816642999649048, 0.26821279525756836, 0.23356106877326965, 0.28116127848625183, 0.16717961430549622, 0.23265916109085083, 0.20872485637664795, 0.23910926282405853, 0.1896253377199173, 0.1703248769044876, 0.28243815898895264, 0.19576141238212585, 0.25669845938682556, 0.2114538848400116, 0.223032146692276, 0.2112353891134262, 0.27433693408966064, 0.2358197718858719, 0.2091229259967804, 0.25360122323036194, 0.2435162514448166, 0.21880237758159637, 0.23826737701892853, 0.26426029205322266, 0.26431962847709656, 0.26917800307273865, 0.2770632803440094, 0.30584827065467834, 0.18724308907985687, 0.24218493700027466, 0.19899219274520874, 0.27186813950538635, 0.25521159172058105, 0.24890968203544617, 0.2482033222913742, 0.2327910214662552, 0.28904521465301514, 0.2506658434867859, 0.25780901312828064, 0.25304335355758667, 0.30149370431900024, 0.1853453367948532, 0.19869272410869598, 0.28291353583335876, 0.18005549907684326, 0.24989688396453857, 0.25237563252449036, 0.26315388083457947, 0.2036094069480896, 0.1939934492111206, 0.22656579315662384, 0.22474299371242523, 0.2270280420780182, 0.2284841537475586, 0.29791128635406494, 0.24701392650604248, 2.9523472785949707, 4.492173194885254, 2.7952327728271484, 3.498350143432617, 3.2444310188293457, 2.061680793762207, 4.008265495300293, 2.078111171722412, 2.4459590911865234, 3.5673587322235107, 2.973085880279541, 3.8047280311584473, 3.169287919998169, 2.581411361694336, 1.8896770477294922, 2.649257183074951, 2.8923611640930176, 3.316370964050293, 3.56148362159729, 3.597527027130127, 2.6501619815826416, 2.635364294052124, 2.4930970668792725, 1.4788241386413574, 1.9666149616241455, 3.1337108612060547, 3.225922107696533, 2.2143478393554688, 3.8385496139526367, 2.1853017807006836, 2.9748265743255615, 2.0794923305511475, 3.184192419052124, 2.6007983684539795, 2.4210121631622314, 5.619016170501709, 3.5788514614105225, 2.15002703666687, 3.8158485889434814, 2.5282516479492188, 1.7370513677597046, 2.687744140625, 4.106894016265869, 3.3915374279022217, 2.7079429626464844, 2.23311448097229, 3.4962401390075684, 3.595775604248047, 3.575244665145874, 2.4675135612487793, 2.6948752403259277, 2.5571789741516113, 3.146409749984741, 4.35911226272583, 2.663466691970825, 2.229787826538086, 4.524866104125977, 4.106805801391602, 3.6973254680633545, 2.652031183242798, 4.084209442138672, 3.328477621078491, 3.0026040077209473, 2.082110643386841, 3.421206474304199, 2.3115146160125732, 2.735088348388672, 2.713857650756836, 2.9460203647613525, 4.374895095825195, 3.1102421283721924, 4.516040325164795, 2.154233932495117, 3.1280763149261475, 2.6890175342559814, 2.1835622787475586, 3.2179739475250244, 2.0672707557678223, 2.619737386703491, 3.954460620880127, 2.838679790496826, 2.8138656616210938, 2.2923545837402344, 3.654222249984741, 3.465381383895874, 3.3019349575042725, 1.8855094909667969, 3.0936388969421387, 3.6896121501922607, 3.453343391418457, 2.9756417274475098, 3.7517199516296387, 2.7933850288391113, 2.4823901653289795, 3.7049496173858643, 2.7293877601623535, 2.5242972373962402, 2.348245143890381, 3.0684704780578613, 2.4565484523773193, 3.8059544563293457, 3.3583438396453857, 3.1589696407318115, 2.8332817554473877, 3.6968600749969482, 3.335339307785034, 5.19091796875, 2.229206085205078, 1.645476222038269, 1.9342697858810425, 2.8716049194335938, 3.1723709106445312, 3.970414400100708, 3.037132740020752, 2.250761032104492, 3.577836275100708, 2.761603355407715, 2.480027914047241, 3.0541985034942627, 2.9069950580596924, 3.427537202835083, 3.547711133956909, 2.7897753715515137, 2.4578213691711426, 2.937941789627075, 2.201341390609741, 3.3138222694396973, 2.2563822269439697, 3.0638363361358643, 2.2908835411071777, 2.461148500442505, 2.1700704097747803, 3.0822930335998535, 2.9889659881591797, 2.652085781097412, 3.1849746704101562, 3.4801406860351562, 3.057997465133667, 2.911529541015625, 2.1112897396087646, 2.7738137245178223, 3.264982223510742, 3.5762321949005127, 3.3502378463745117, 3.38211989402771, 2.7889251708984375, 2.3041796684265137, 2.5318002700805664, 3.178182601928711, 2.9793901443481445, 2.653179883956909, 2.1909618377685547, 2.5423941612243652, 3.944952964782715, 3.4168248176574707, 2.6777684688568115, 2.733032703399658, 2.6493759155273438, 2.6567583084106445, 2.5444822311401367, 3.65417218208313, 2.25761079788208, 3.173684597015381, 2.527177095413208, 3.305058002471924, 2.0947561264038086, 2.5443999767303467, 2.313251256942749, 3.2085652351379395, 2.828792095184326, 3.9836196899414062, 1.542197585105896, 3.651231527328491, 3.4954288005828857, 2.5984947681427, 3.2307815551757812, 4.155895233154297, 1.7370439767837524, 2.272059440612793, 1.9291868209838867, 2.433978319168091, 2.7590737342834473, 3.4308106899261475, 1.921531319618225, 3.2899270057678223, 3.666102170944214, 1.9349074363708496, 3.662156343460083, 2.4963667392730713, 2.9611480236053467, 3.261089324951172, 3.5182735919952393, 2.4478464126586914, 3.1044185161590576, 2.782252073287964, 3.002178192138672, 2.876570463180542, 2.499788999557495, 3.050616979598999, 3.210984945297241, 2.6061458587646484, 2.055739164352417, 1.6397879123687744, 3.6885578632354736, 3.1508471965789795, 2.5794243812561035, 4.418655872344971, 4.011890888214111, 2.345445156097412, 1.9281885623931885, 3.341534376144409, 2.9354488849639893, 2.315727710723877, 3.523979663848877, 2.2721943855285645, 3.1803512573242188, 5.327330112457275, 2.390608310699463, 2.742401599884033, 3.531749725341797, 2.528461456298828, 2.6107499599456787, 3.3912477493286133, 3.1803505420684814, 2.386414051055908, 3.1186909675598145, 1.971954345703125, 3.061553955078125, 2.442537784576416, 3.586761474609375, 2.243851900100708, 2.4928805828094482, 2.086881160736084, 2.2470738887786865, 4.142417907714844, 2.0013139247894287, 1.532603144645691, 2.485069751739502, 3.18215274810791, 2.2130813598632812, 3.7972216606140137, 1.8096593618392944, 3.510995388031006, 3.866368532180786, 2.3399717807769775, 2.590740919113159, 2.5650134086608887, 3.078538656234741, 1.8339636325836182, 2.7111096382141113, 3.416714906692505, 1.6468805074691772, 2.859095335006714, 3.3032732009887695, 2.513404130935669, 2.481051445007324, 2.3519198894500732, 3.023705005645752, 4.406234264373779, 4.399454116821289, 3.108441114425659, 2.82926869392395, 3.694727897644043, 2.3891639709472656, 2.9175503253936768, 3.184629440307617, 3.6497442722320557, 2.9680192470550537, 2.94183087348938, 2.0971438884735107, 2.8015575408935547, 2.4235076904296875, 1.8091375827789307, 2.460846185684204, 2.8528473377227783, 1.8380990028381348, 2.0191283226013184, 1.5827583074569702, 2.6549739837646484, 2.444103240966797, 2.5759410858154297, 3.4881343841552734, 2.137542724609375, 1.8475737571716309, 4.2174530029296875, 2.290045976638794, 3.259706974029541, 3.5241570472717285, 3.2523903846740723, 2.959761381149292, 3.700516939163208, 2.186408758163452, 2.129755973815918, 3.2969987392425537, 3.101156234741211, 2.86466383934021, 2.7674179077148438, 3.1983025074005127, 2.831799268722534, 2.829646587371826, 265.27557373046875, 150.77642822265625, 42.9947509765625, 107.93390655517578, 211.32347106933594, 234.07472229003906, 226.05859375, 116.36876678466797, 249.94952392578125, 214.72528076171875, 514.3370361328125, 409.9872131347656, 263.9373779296875, 349.15093994140625, 145.54823303222656, 276.4482421875, 288.4767761230469, 264.6264343261719, 226.54161071777344, 138.2482147216797, 101.71952819824219, 117.49224090576172, 123.75146484375, 197.75694274902344, 156.8135528564453, 70.714599609375, 194.67718505859375, 578.4625854492188, 195.5745391845703, 175.5504608154297, 101.24515533447266, 194.60968017578125, 238.08908081054688, 256.4075927734375, 167.7505645751953, 322.3528137207031, 162.98399353027344, 82.99053192138672, 267.1892395019531, 280.9505310058594, 110.01953125, 129.259521484375, 54.7607421875, 245.4828643798828, 337.0838928222656, 48.00244140625, 143.26806640625, 40.419532775878906, 225.47325134277344, 108.75128936767578, 103.9154052734375, 316.8478088378906, 396.7923889160156, 470.15130615234375, 151.658935546875, 139.94024658203125, 228.70773315429688, 458.4564208984375, 140.75018310546875, 544.5931396484375, 320.63836669921875, 213.56103515625, 119.030029296875, 93.75074005126953, 47.5, 382.20062255859375, 463.9201354980469, 125.24530029296875, 98.95581817626953, 199.8321075439453, 217.63992309570312, 323.77056884765625, 240.49053955078125, 191.06280517578125, 79.93047332763672, 85.91766357421875, 84.74903869628906, 66.2606430053711, 238.820068359375, 216.591796875, 111.87417602539062, 368.9072265625, 259.4746398925781, 376.1154479980469, 262.79315185546875, 512.3084106445312, 461.623046875, 146.252197265625, 127.49530029296875, 275.3631591796875, 298.58245849609375, 160.11289978027344, 276.5822448730469, 220.5637969970703, 173.98577880859375, 220.2138671875, 278.68194580078125, 433.096435546875, 85.05999755859375, 144.70364379882812, 253.91143798828125, 149.84356689453125, 114.48211669921875, 255.08914184570312, 176.5096435546875, 342.25396728515625, 371.3161926269531, 297.4778747558594, 49.73540115356445, 237.1288299560547, 409.4930114746094, 179.4978790283203, 233.1834716796875, 182.4870147705078, 351.4249572753906, 108.48553466796875, 214.78819274902344, 394.9186706542969, 563.3716430664062, 380.5666198730469, 114.51737213134766, 270.6094055175781, 272.373046875, 303.193359375, 180.01715087890625, 409.56787109375, 115.46728515625, 85.43377685546875, 153.53775024414062, 210.8159942626953, 68.82502746582031, 277.2441711425781, 328.0724182128906, 75.19886016845703, 300.90283203125, 170.36679077148438, 79.626708984375, 195.55010986328125, 105.4855728149414, 55.5606689453125, 113.5426254272461, 85.8212890625, 138.73109436035156, 175.18832397460938, 392.7645263671875, 133.46710205078125, 380.7356262207031, 143.33460998535156, 312.1769714355469, 46.412166595458984, 159.04339599609375, 312.82781982421875, 138.4062042236328, 54.167724609375, 342.7181701660156, 115.14706420898438, 81.1915283203125, 326.76959228515625, 102.99372863769531, 148.830078125, 505.0274963378906, 180.48057556152344, 72.322509765625, 163.5360107421875, 453.7687072753906, 222.11203002929688, 436.3544006347656, 89.23644256591797, 251.13291931152344, 45.535614013671875, 302.28973388671875, 80.06533813476562, 283.01495361328125, 273.6158447265625, 127.6053466796875, 351.5162353515625, 96.15960693359375, 56.16717529296875, 401.6418151855469, 376.4761657714844, 190.64866638183594, 81.68297576904297, 290.7220458984375, 326.3693542480469, 197.70713806152344, 308.1007080078125, 280.1693115234375, 436.3414611816406, 342.59765625, 127.81005859375, 311.8927917480469, 93.195556640625, 424.7794494628906, 325.81805419921875, 206.0476837158203, 147.20460510253906, 71.423828125, 167.52587890625, 70.06781768798828, 113.58182525634766, 103.13797760009766, 68.87476348876953, 746.1174926757812, 63.50091552734375, 149.4984130859375, 153.3114013671875, 75.61181640625, 57.987117767333984, 120.76656341552734, 170.8466339111328, 238.2291717529297, 86.5379638671875, 182.92930603027344, 46.61158752441406, 65.12480926513672, 253.1474609375, 282.6789855957031, 139.9373779296875, 354.146484375, 247.25889587402344, 252.68585205078125, 213.40126037597656, 271.0500183105469, 119.51866912841797, 297.2691650390625, 226.3054656982422, 148.53746032714844, 422.88372802734375, 194.85401916503906, 136.34873962402344, 160.40028381347656, 78.04621124267578, 294.2225646972656, 63.7901611328125, 297.54876708984375, 174.1240997314453, 65.9305419921875, 141.88107299804688, 185.15185546875, 145.21229553222656, 294.369140625, 153.30984497070312, 715.321533203125, 176.70957946777344, 45.5164794921875, 266.43682861328125, 203.95433044433594, 299.7557678222656, 316.38092041015625, 349.1915588378906, 129.91615295410156, 356.7749938964844, 116.7975845336914, 386.7013244628906, 248.7896270751953, 384.6617431640625, 371.0167541503906, 264.01025390625, 103.37606811523438, 133.4077911376953, 56.40594482421875, 187.04054260253906, 430.9005432128906, 53.193172454833984, 216.48699951171875, 294.9577941894531, 457.10546875, 90.5238037109375, 110.183837890625, 84.2733154296875, 435.7672424316406, 373.220458984375, 518.42138671875, 110.518798828125, 220.76214599609375, 54.44427490234375, 211.35060119628906, 442.9269104003906, 254.50531005859375, 154.272216796875, 201.10018920898438, 584.6435546875, 256.8078918457031, 155.4991912841797, 223.0650177001953, 139.183349609375, 312.46826171875, 234.00205993652344, 338.7211608886719, 400.5963134765625, 288.36328125, 70.37642669677734, 248.20831298828125, 340.3426208496094, 124.77728271484375, 176.88121032714844, 129.66920471191406, 252.7720489501953, 61.286991119384766, 107.97943115234375, 3.447781801223755, 2.493304491043091, 2.8962297439575195, 2.9694244861602783, 2.4036009311676025, 2.1078882217407227, 2.1706228256225586, 2.1816701889038086, 1.92027747631073, 2.5590603351593018, 2.6608898639678955, 3.4974381923675537, 2.8825836181640625, 3.399324655532837, 2.118536949157715, 2.815812349319458, 2.729609966278076, 1.892304539680481, 1.6738024950027466, 3.119511127471924, 4.184842586517334, 2.2066071033477783, 1.1843293905258179, 1.8949919939041138, 1.9194082021713257, 2.2216339111328125, 1.8325928449630737, 2.8059582710266113, 1.5591154098510742, 2.8725662231445312, 3.240023612976074, 2.0899877548217773, 2.2228522300720215, 2.61517596244812, 4.117728233337402, 2.2510085105895996, 2.118332862854004, 3.1199429035186768, 2.5264511108398438, 2.4906251430511475, 2.061849594116211, 1.6497373580932617, 2.605074405670166, 2.9201900959014893, 2.2363481521606445, 2.8031749725341797, 2.9740312099456787, 1.5385470390319824, 2.6380531787872314, 2.032050132751465, 2.941049814224243, 1.8409719467163086, 2.3738694190979004, 2.3675622940063477, 1.6359457969665527, 3.172595739364624, 1.3313230276107788, 3.2086424827575684, 1.4048360586166382, 2.5812249183654785, 2.170670509338379, 3.6548004150390625, 2.487671375274658, 2.302353620529175, 3.302964448928833, 3.2964160442352295, 2.134544610977173, 2.1544973850250244, 3.3978893756866455, 3.5800352096557617, 2.7775375843048096, 2.2429704666137695, 1.77104651927948, 2.862919807434082, 2.9333858489990234, 3.0683300495147705, 3.1900622844696045, 3.0310351848602295, 3.120060920715332, 2.771289110183716, 2.497912645339966, 3.8244221210479736, 2.472304105758667, 2.2411842346191406, 2.7828571796417236, 2.2373669147491455, 1.8982572555541992, 2.411372423171997, 3.095017671585083, 2.431759834289551, 2.4058620929718018, 3.4257311820983887, 3.1473305225372314, 2.724928140640259, 2.880643129348755, 3.2213823795318604, 2.519153118133545, 2.6251091957092285, 2.157771110534668, 2.115231513977051, 2.4091391563415527, 2.018369436264038, 3.181473970413208, 2.4360790252685547, 3.072845458984375, 3.1204826831817627, 3.359278678894043, 2.5203888416290283, 1.6173086166381836, 1.9478874206542969, 2.967728853225708, 2.9497032165527344, 2.4082326889038086, 2.6785309314727783, 1.724601149559021, 2.623530626296997, 4.072830677032471, 2.5242738723754883, 4.189677715301514, 3.584418296813965, 2.613776206970215, 3.4756157398223877, 3.366755962371826, 3.0119717121124268, 1.7560616731643677, 2.6381444931030273, 2.605340003967285, 2.6186513900756836, 3.5879392623901367, 3.1075830459594727, 3.631629467010498, 3.62701153755188, 2.0632829666137695, 3.4693784713745117, 3.992842674255371, 3.0243120193481445, 2.007136344909668, 2.4284706115722656, 2.9186198711395264, 2.6559484004974365, 2.542189359664917, 3.3393478393554688, 2.1333913803100586, 1.548378825187683, 3.4039392471313477, 3.3794004917144775, 1.1935710906982422, 2.5859127044677734, 3.3632421493530273, 2.9156253337860107, 2.4902005195617676, 2.048142433166504, 1.841158390045166, 3.541483163833618, 2.3169403076171875, 1.20249342918396, 3.3579094409942627, 3.4954192638397217, 1.9096194505691528, 2.391341209411621, 3.3025081157684326, 3.6821866035461426, 1.8510621786117554, 2.5039291381835938, 3.3607304096221924, 3.261906623840332, 1.3449695110321045, 1.95557701587677, 2.2031307220458984, 2.619368314743042, 1.6719207763671875, 3.503751039505005, 2.168766975402832, 2.701693058013916, 2.0971453189849854, 2.488032341003418, 3.405038356781006, 2.9468414783477783, 3.3809916973114014, 2.2439184188842773, 2.268252372741699, 2.0073347091674805, 2.7011687755584717, 3.2222511768341064, 1.5618621110916138, 2.166947364807129, 2.7835168838500977, 3.5495989322662354, 3.7515783309936523, 2.61135196685791, 3.568457841873169, 2.931157112121582, 2.691852569580078, 2.4687018394470215, 1.4797030687332153, 1.8593415021896362, 3.696820020675659, 2.407658576965332, 2.750037431716919, 3.1031606197357178, 3.250779867172241, 4.068600177764893, 2.4975576400756836, 2.605273485183716, 2.5529987812042236, 3.7850587368011475, 3.399883985519409, 2.7342474460601807, 2.566075325012207, 2.052600145339966, 2.568758249282837, 1.7058748006820679, 3.6051206588745117, 2.5755341053009033, 2.002671718597412, 3.151045560836792, 3.1498324871063232, 2.1054043769836426, 2.5852372646331787, 1.744863510131836, 2.4000673294067383, 1.3719323873519897, 3.4060750007629395, 2.112595796585083, 2.5208261013031006, 2.9139244556427, 2.886272430419922, 2.6318199634552, 2.3608834743499756, 3.050123929977417, 2.8558456897735596, 3.0194835662841797, 1.457892894744873, 3.6133320331573486, 2.7975378036499023, 3.351452589035034, 2.0832412242889404, 2.4324755668640137, 3.804694175720215, 2.9683640003204346, 3.8358776569366455, 2.7556722164154053, 2.8380348682403564, 2.751314878463745, 1.486642599105835, 2.7613766193389893, 2.308712959289551, 3.1624362468719482, 2.009881019592285, 2.6709206104278564, 2.4649152755737305, 3.5084409713745117, 2.3443422317504883, 3.4437572956085205, 2.081679344177246, 2.493208646774292, 2.2838521003723145, 2.4645345211029053, 2.1782193183898926, 1.8828496932983398, 3.7520854473114014, 2.613476514816284, 3.7376396656036377, 3.714235782623291, 3.0317540168762207, 2.412869453430176, 1.3597155809402466, 2.082125425338745, 2.485527992248535, 2.562413215637207, 2.1098241806030273, 2.3173446655273438, 2.8860864639282227, 4.052581787109375, 2.192042589187622, 2.8994991779327393, 2.804427146911621, 3.8147382736206055, 2.783250093460083, 2.439739227294922, 2.657670736312866, 3.82171368598938, 2.8374974727630615, 2.7902255058288574, 3.3404946327209473, 2.300147294998169, 2.5788280963897705, 3.039715528488159, 3.0701873302459717, 1.993519902229309, 1.2991231679916382, 2.1971371173858643, 2.998433828353882, 2.2852983474731445, 4.045466423034668, 3.627239942550659, 3.276662588119507, 3.2954323291778564, 3.363210678100586, 2.9647741317749023, 0.2291613668203354, 0.18970887362957, 0.23319292068481445, 0.22696788609027863, 0.30947399139404297, 0.20680594444274902, 0.21554014086723328, 0.2116910070180893, 0.27026939392089844, 0.27438217401504517, 0.23413066565990448, 0.24446454644203186, 0.25224465131759644, 0.2542656362056732, 0.2677082419395447, 0.17665444314479828, 0.3059988021850586, 0.2494259774684906, 0.26422327756881714, 0.2485864758491516, 0.24776999652385712, 0.20864005386829376, 0.3167760670185089, 0.24018894135951996, 0.20953254401683807, 0.22559690475463867, 0.1819262057542801, 0.3140944540500641, 0.21987085044384003, 0.25517722964286804, 0.24059167504310608, 0.24122993648052216, 0.26791149377822876, 0.20489443838596344, 0.19638267159461975, 0.288432240486145, 0.23245859146118164, 0.2616245150566101, 0.2152918577194214, 0.19873635470867157, 0.2204752266407013, 0.25928571820259094, 0.20015078783035278, 0.25160151720046997, 0.24761904776096344, 0.21042826771736145, 0.27687254548072815, 0.22616662085056305, 0.27480971813201904, 0.2380838394165039, 0.24381960928440094, 0.20349420607089996, 0.21930983662605286, 0.24743886291980743, 0.26754480600357056, 0.24613967537879944, 0.2913236916065216, 0.2164873480796814, 0.2572777569293976, 0.2827777862548828, 0.3140369653701782, 0.29923635721206665, 0.22733967006206512, 0.20863468945026398, 0.2859812378883362, 0.1948244422674179, 0.20872777700424194, 0.22770099341869354, 0.22803664207458496, 0.25709643959999084, 0.30860674381256104, 0.15014715492725372, 0.2478829175233841, 0.2186143696308136, 0.2362890988588333, 0.2861161231994629, 0.30189940333366394, 0.3238542973995209, 0.3114017844200134, 0.23116916418075562, 0.22718581557273865, 0.25844907760620117, 0.22784097492694855, 0.2869015038013458, 0.23754236102104187, 0.23142163455486298, 0.26903536915779114, 0.20305560529232025, 0.2492428869009018, 0.1729445457458496, 0.20233458280563354, 0.2647918164730072, 0.2133399099111557, 0.26102015376091003, 0.2745833992958069, 0.2161456197500229, 0.24702133238315582, 0.27888602018356323, 0.3086302578449249, 0.30999940633773804, 0.2431637942790985, 0.20252712070941925, 0.21451148390769958, 0.28458738327026367, 0.2944798171520233, 0.25086069107055664, 0.2514788508415222, 0.2636600732803345, 0.24079318344593048, 0.3055613934993744, 0.24024218320846558, 0.2458408921957016, 0.28363656997680664, 0.32106512784957886, 0.26251891255378723, 0.29081666469573975, 0.29088473320007324, 0.2664090394973755, 0.23939773440361023, 0.2506982088088989, 0.27693337202072144, 0.25172698497772217, 0.28155162930488586, 0.22010894119739532, 0.259733110666275, 0.28272342681884766, 0.3218856751918793, 0.2864862084388733, 0.24231161177158356, 0.23809020221233368, 0.24842782318592072, 0.2964666783809662, 0.24311399459838867, 0.22794024646282196, 0.19938190281391144, 0.22935108840465546, 0.25986185669898987, 0.2308051437139511, 0.2577381134033203, 0.24257326126098633, 0.24792972207069397, 0.19988654553890228, 0.258379191160202, 0.2516826093196869, 0.2791290879249573, 0.23474571108818054, 0.2514919340610504, 0.2558683454990387, 0.2641528248786926, 0.29002702236175537, 0.2759983539581299, 0.22257563471794128, 0.20801383256912231, 0.24881282448768616, 0.2219703197479248, 0.269233375787735, 0.2558169960975647, 0.2433559149503708, 0.29708361625671387, 0.23981210589408875, 0.2528313398361206, 0.20252496004104614, 0.230048269033432, 0.26010623574256897, 0.23413866758346558, 0.2613149583339691, 0.2615697383880615, 0.173639714717865, 0.2783561944961548, 0.2688380479812622, 0.22016984224319458, 0.2795141041278839, 0.18513117730617523, 0.20490212738513947, 0.22857727110385895, 0.2975817918777466, 0.20579832792282104, 0.234071284532547, 0.25669050216674805, 0.19523751735687256, 0.3158467411994934, 0.2059209793806076, 0.2615315914154053, 0.2086791694164276, 0.2332165241241455, 0.2536712884902954, 0.2120959758758545, 0.2721494138240814, 0.19233958423137665, 0.26547354459762573, 0.25266093015670776, 0.21663948893547058, 0.2155793160200119, 0.243976891040802, 0.21196754276752472, 0.22206948697566986, 0.2623138427734375, 0.2560853660106659, 0.2805013954639435, 0.2938890755176544, 0.284727543592453, 0.2366541177034378, 0.23715782165527344, 0.2067347913980484, 0.26274919509887695, 0.2586696445941925, 0.21790064871311188, 0.2363017201423645, 0.29679256677627563, 0.19437634944915771, 0.250318706035614, 0.2515483498573303, 0.2403663545846939, 0.2868146002292633, 0.22026601433753967, 0.31058090925216675, 0.19617518782615662, 0.2580937445163727, 0.2236696183681488, 0.24359843134880066, 0.23583823442459106, 0.2012920379638672, 0.2553618550300598, 0.2623078525066376, 0.31021544337272644, 0.3515194356441498, 0.27184566855430603, 0.3103659451007843, 0.16117297112941742, 0.21544505655765533, 0.2993386685848236, 0.18261899054050446, 0.2542111277580261, 0.22434282302856445, 0.21518826484680176, 0.2169312983751297, 0.2222660332918167, 0.23384211957454681, 0.17300231754779816, 0.2553060054779053, 0.20022276043891907, 0.2405063509941101, 0.26867014169692993, 0.21688449382781982, 0.2152373492717743, 0.23809973895549774, 0.21011614799499512, 0.27840593457221985, 0.3264404237270355, 0.22829407453536987, 0.20218627154827118, 0.2312874048948288, 0.2344868779182434, 0.2321634292602539, 0.17445498704910278, 0.23098941147327423, 0.2702352702617645, 0.2220519632101059, 0.21235959231853485, 0.25174009799957275, 0.22167176008224487, 0.2738233208656311, 0.24996855854988098, 0.21349450945854187, 0.17384374141693115, 0.2937243580818176, 0.254952609539032, 0.20630908012390137, 0.25480541586875916, 0.17857180535793304, 0.20057128369808197, 0.203724667429924, 0.24440741539001465, 0.24229905009269714, 0.2421332150697708, 0.253781795501709, 0.25908708572387695, 0.20354782044887543, 0.24664030969142914, 0.22179313004016876, 0.29453107714653015, 0.253597617149353, 0.2606596052646637, 0.20286746323108673, 0.22922438383102417, 0.24269598722457886, 0.2565484642982483, 0.3005913496017456, 0.2565646171569824, 0.30591335892677307, 0.2466677874326706, 0.23582413792610168, 0.23630622029304504, 0.2178770899772644, 0.22432081401348114, 0.2606431245803833, 0.23345084488391876, 0.23916207253932953, 0.22293923795223236, 0.2657788395881653, 3.0806756019592285, 2.1853420734405518, 2.5490331649780273, 2.250720262527466, 2.2563695907592773, 3.7102444171905518, 3.3721494674682617, 4.201451778411865, 2.3261609077453613, 4.220310688018799, 2.5791594982147217, 2.960354804992676, 4.206275463104248, 2.5679948329925537, 2.4581503868103027, 1.9387187957763672, 2.8614373207092285, 2.3047964572906494, 3.3740932941436768, 2.98785400390625, 2.9324710369110107, 1.6248221397399902, 3.008122682571411, 3.9034981727600098, 3.1925933361053467, 2.9997997283935547, 4.039950847625732, 2.40057373046875, 2.4843554496765137, 2.171884298324585, 4.615699768066406, 4.013216018676758, 2.4470229148864746, 2.484954833984375, 4.63624906539917, 3.5163238048553467, 2.9336767196655273, 3.9950497150421143, 2.9760148525238037, 3.5462570190429688, 2.3134689331054688, 3.3801848888397217, 3.6296169757843018, 2.4347753524780273, 2.904533863067627, 2.9268553256988525, 2.2015461921691895, 3.743589401245117, 2.9291186332702637, 3.221228837966919, 3.42278790473938, 3.2212436199188232, 3.677445650100708, 2.3320140838623047, 2.218329668045044, 2.3057620525360107, 2.5217297077178955, 1.9267733097076416, 3.739274740219116, 2.7655892372131348, 2.6142807006835938, 3.3742828369140625, 3.23083233833313, 3.370699882507324, 2.6542346477508545, 2.43698787689209, 3.863741874694824, 3.289260149002075, 3.87884259223938, 4.077502727508545, 2.400115489959717, 3.4843661785125732, 2.706158399581909, 3.231865406036377, 2.943385601043701, 2.9368724822998047, 5.002401351928711, 3.7618865966796875, 2.4968318939208984, 4.396762371063232, 4.3645172119140625, 3.1231460571289062, 3.630117416381836, 3.202141284942627, 2.062006711959839, 2.86443829536438, 4.684320449829102, 2.9083659648895264, 3.328587770462036, 4.011540412902832, 2.4219613075256348, 2.9826691150665283, 3.9862425327301025, 2.617621421813965, 4.133835315704346, 2.6024365425109863, 3.7995803356170654, 3.599165678024292, 2.7820866107940674, 3.896467924118042, 3.502758741378784, 3.4736886024475098, 3.5682318210601807, 2.584043502807617, 2.7005972862243652, 3.029568910598755, 1.9400542974472046, 3.563188314437866, 3.2803332805633545, 2.7459733486175537, 3.6735711097717285, 3.3433620929718018, 1.825730562210083, 2.146925687789917, 3.4584226608276367, 3.9769127368927, 3.2431461811065674, 2.5037529468536377, 2.153742790222168, 2.913635730743408, 2.413409471511841, 3.1895954608917236, 2.2252798080444336, 3.161510467529297, 2.2500128746032715, 2.5184993743896484, 2.2049005031585693, 2.1723365783691406, 2.794708728790283, 2.9464995861053467, 2.6670162677764893, 2.267937183380127, 4.229123592376709, 2.6138970851898193, 2.1936938762664795, 3.0409493446350098, 2.2167065143585205, 3.1258533000946045, 2.933605194091797, 4.101044654846191, 3.686124086380005, 2.1712863445281982, 2.3322348594665527, 3.158726453781128, 2.8166604042053223, 2.6007909774780273, 3.4802608489990234, 2.0703046321868896, 3.39621901512146, 3.5065999031066895, 2.6335396766662598, 2.800511598587036, 2.461354970932007, 2.1705703735351562, 4.155386447906494, 2.8501880168914795, 2.6015100479125977, 3.289605140686035, 3.0929455757141113, 1.7124313116073608, 2.7242064476013184, 5.597499847412109, 3.226625919342041, 2.975295305252075, 2.9825243949890137, 2.614530563354492, 1.9992384910583496, 3.5693864822387695, 2.56856107711792, 3.7483716011047363, 2.55950927734375, 2.1604082584381104, 3.5958962440490723, 1.848457932472229, 3.314577579498291, 2.182577133178711, 2.3411357402801514, 1.8371868133544922, 1.8270149230957031, 3.712050199508667, 3.450829029083252, 3.2263734340667725, 3.6225955486297607, 3.6659092903137207, 2.46203351020813, 2.0256383419036865, 3.5421528816223145, 3.3474011421203613, 3.053361654281616, 2.7022926807403564, 2.0646798610687256, 2.93845272064209, 2.3550050258636475, 2.506807565689087, 4.970436096191406, 4.1857147216796875, 2.1613194942474365, 3.1537506580352783, 3.288280487060547, 3.1630876064300537, 2.158393621444702, 3.504459857940674, 3.3377654552459717, 1.6410890817642212, 3.499969959259033, 3.881390333175659, 2.7168948650360107, 4.304409980773926, 2.508347749710083, 2.8964314460754395, 2.4210023880004883, 3.521132230758667, 3.361469030380249, 1.9584728479385376, 2.1781017780303955, 2.407604217529297, 3.8409423828125, 3.5236637592315674, 3.0969481468200684, 4.1241583824157715, 2.150440216064453, 3.860549211502075, 3.978029727935791, 2.5971696376800537, 2.2184362411499023, 1.8757582902908325, 3.861452579498291, 1.9892516136169434, 1.435392141342163, 3.585366725921631, 2.582456588745117, 2.714933395385742, 2.343381881713867, 2.9684014320373535, 2.6006152629852295, 3.6735715866088867, 2.7853493690490723, 2.1821422576904297, 2.845335006713867, 3.7556262016296387, 3.086061954498291, 1.9987760782241821, 2.6611857414245605, 3.2480132579803467, 3.5294036865234375, 2.5321459770202637, 2.0331168174743652, 3.7139739990234375, 3.1372456550598145, 2.9888267517089844, 2.4565141201019287, 3.1570701599121094, 2.0968949794769287, 2.8157384395599365, 1.896706223487854, 3.7419536113739014, 4.479800701141357, 3.0642716884613037, 2.889695405960083, 3.497673511505127, 4.437363624572754, 3.6973705291748047, 3.8494396209716797, 2.8303310871124268, 2.91904878616333, 2.391305685043335, 4.1775054931640625, 3.5367648601531982, 4.742271423339844, 1.7928504943847656, 2.8705570697784424, 2.9749772548675537, 2.4822998046875, 2.482586622238159, 3.3182640075683594, 2.466810941696167, 3.077476978302002, 1.6660970449447632, 3.84793758392334, 3.6900079250335693, 3.3529727458953857, 3.5647289752960205, 3.391170024871826, 3.4659199714660645, 2.9539196491241455, 2.932994842529297, 3.5341503620147705, 2.257601499557495, 2.678453207015991, 3.275803804397583, 1.6009159088134766, 2.6680638790130615, 3.993011951446533, 3.535759449005127, 3.8929684162139893, 3.5619149208068848, 1.9239463806152344, 3.8140995502471924, 2.1468257904052734, 3.2221195697784424, 235.5209503173828, 220.56118774414062, 72.78472137451172, 86.45624542236328, 123.17063903808594, 82.044921875, 183.72317504882812, 139.35284423828125, 295.3814697265625, 203.40164184570312, 457.8254699707031, 316.77337646484375, 102.9285888671875, 262.45074462890625, 219.63980102539062, 325.7945556640625, 75.48992919921875, 48.9293098449707, 187.50218200683594, 252.07733154296875, 88.0309066772461, 468.070068359375, 188.3994903564453, 236.0086212158203, 91.71795654296875, 119.32296752929688, 233.88890075683594, 204.2090606689453, 442.28460693359375, 229.0321502685547, 510.4730224609375, 180.13232421875, 241.14697265625, 95.84988403320312, 140.6438751220703, 258.46099853515625, 314.531982421875, 39.38616943359375, 273.1242370605469, 159.50491333007812, 195.2982940673828, 59.2451171875, 312.4002685546875, 207.96728515625, 203.6532745361328, 70.65640258789062, 194.39874267578125, 69.64691162109375, 58.20858383178711, 86.23095703125, 296.014892578125, 95.96773529052734, 167.19837951660156, 130.91033935546875, 446.50518798828125, 533.0316162109375, 193.1590576171875, 105.43666076660156, 349.977294921875, 321.1716613769531, 285.75445556640625, 443.26702880859375, 94.21597290039062, 250.3623809814453, 236.80804443359375, 593.8758544921875, 122.53292083740234, 53.63141632080078, 109.36248016357422, 128.9281463623047, 197.1892547607422, 439.8719482421875, 225.0720977783203, 188.63609313964844, 363.2450256347656, 181.4632568359375, 333.0146484375, 53.38191223144531, 56.52478790283203, 248.6464080810547, 203.2834014892578, 178.9610137939453, 213.68310546875, 117.76409912109375, 90.5685806274414, 696.30419921875, 432.8000183105469, 596.1566772460938, 234.11964416503906, 85.26708984375, 241.03045654296875, 179.28135681152344, 85.55030822753906, 168.2254638671875, 64.0841064453125, 424.494873046875, 143.13194274902344, 313.6016845703125, 461.0438537597656, 202.96739196777344, 340.073974609375, 192.31005859375, 191.18418884277344, 220.9730224609375, 55.730281829833984, 133.5262451171875, 216.92971801757812, 113.3319320678711, 255.72720336914062, 297.7070007324219, 126.514892578125, 548.9796142578125, 352.5074157714844, 63.70178985595703, 414.8390197753906, 681.2726440429688, 178.4688262939453, 206.0023193359375, 90.8125, 209.44091796875, 52.2542724609375, 89.4879150390625, 79.51860809326172, 158.74493408203125, 190.1102294921875, 126.2675552368164, 156.91064453125, 147.19764709472656, 486.1854553222656, 244.97479248046875, 392.85943603515625, 357.8543395996094, 390.3287658691406, 246.05484008789062, 104.803466796875, 327.4910888671875, 240.9716796875, 55.015869140625, 237.07835388183594, 126.92138671875, 300.81536865234375, 312.225341796875, 184.3055419921875, 228.62071228027344, 456.725341796875, 269.7926330566406, 444.9164733886719, 327.1395568847656, 239.334716796875, 130.14393615722656, 208.00018310546875, 300.5901794433594, 201.5694122314453, 51.80923080444336, 514.365966796875, 133.380126953125, 164.3563232421875, 353.82647705078125, 100.27208709716797, 262.74407958984375, 201.73367309570312, 175.57382202148438, 83.2362060546875, 261.5002136230469, 277.99951171875, 53.1929931640625, 390.59765625, 266.8497314453125, 369.8013916015625, 438.12646484375, 56.2606201171875, 101.52788543701172, 373.099365234375, 191.7313995361328, 270.0360107421875, 124.463623046875, 68.73190307617188, 94.20257568359375, 667.4762573242188, 268.6378173828125, 84.94091796875, 86.5516357421875, 186.87120056152344, 372.2511291503906, 160.59320068359375, 310.09344482421875, 71.73574829101562, 512.5936889648438, 232.24093627929688, 116.69068145751953, 307.8282470703125, 106.53802490234375, 55.92267608642578, 235.27061462402344, 236.57254028320312, 157.9813690185547, 443.1792907714844, 131.4611358642578, 251.7652130126953, 200.25601196289062, 345.92242431640625, 415.2742004394531, 535.8343505859375, 94.96894073486328, 454.9046630859375, 637.4188232421875, 135.84423828125, 92.43116760253906, 144.76365661621094, 179.00302124023438, 120.55634307861328, 207.22979736328125, 204.64761352539062, 45.850341796875, 69.99225616455078, 55.52150344848633, 194.9280548095703, 170.3360137939453, 180.94073486328125, 129.68988037109375, 304.44140625, 220.4716796875, 101.65966796875, 86.63972473144531, 164.4785919189453, 375.73101806640625, 206.76318359375, 168.11839294433594, 103.23605346679688, 360.3377380371094, 232.4899139404297, 401.6181640625, 128.19981384277344, 196.5086669921875, 206.810791015625, 325.02392578125, 326.353515625, 193.34765625, 220.8079833984375, 169.25396728515625, 201.97509765625, 135.82452392578125, 306.1818542480469, 262.9854736328125, 149.6657257080078, 238.89707946777344, 65.122802734375, 388.63409423828125, 196.41506958007812, 130.53814697265625, 145.1496124267578, 317.4818115234375, 58.34065246582031, 68.08049011230469, 199.00205993652344, 314.57904052734375, 247.4832305908203, 129.30335998535156, 131.5104522705078, 120.201171875, 287.89459228515625, 114.566162109375, 102.706787109375, 613.1163330078125, 64.06884002685547, 117.5335693359375, 164.18495178222656, 183.4932403564453, 522.4529418945312, 99.89972686767578, 121.604248046875, 102.2366943359375, 309.0933837890625, 132.01934814453125, 297.7158203125, 61.09637451171875, 251.01097106933594, 347.8702392578125, 156.470703125, 225.14663696289062, 274.03271484375, 160.95680236816406, 123.691162109375, 133.62591552734375, 116.71977996826172, 241.692138671875, 68.82093811035156, 217.57249450683594, 189.6678466796875, 66.9504165649414, 223.9477081298828, 155.38973999023438, 84.86479949951172, 74.76017761230469, 239.5517578125, 283.76953125, 140.5384521484375, 76.99725341796875, 170.7609405517578, 93.8685302734375, 2.5370402336120605, 2.9827892780303955, 3.382317543029785, 2.2257394790649414, 2.6800734996795654, 1.6879808902740479, 2.446549415588379, 2.205282211303711, 3.1681785583496094, 2.242691993713379, 2.4791646003723145, 3.286210298538208, 3.354539632797241, 3.266998291015625, 2.2519633769989014, 2.503859281539917, 2.2250654697418213, 3.4578750133514404, 2.683842658996582, 2.2265536785125732, 2.165684700012207, 2.728461265563965, 2.5028069019317627, 3.898729085922241, 2.795018196105957, 2.101973533630371, 1.8816404342651367, 3.251433849334717, 3.7197606563568115, 3.920292854309082, 3.955652952194214, 2.867205858230591, 3.8527727127075195, 3.1667115688323975, 3.3804867267608643, 1.4142121076583862, 2.13369083404541, 3.0063624382019043, 2.4962451457977295, 4.4023895263671875, 3.981584072113037, 2.8868227005004883, 2.124202251434326, 2.6784965991973877, 2.9999613761901855, 2.170445442199707, 2.5329926013946533, 2.0415947437286377, 3.570050001144409, 2.667172908782959, 2.229074716567993, 2.010523796081543, 1.9153565168380737, 1.681990623474121, 2.0241098403930664, 2.8566136360168457, 1.8082422018051147, 2.3298487663269043, 3.1660079956054688, 3.729976177215576, 2.226872682571411, 3.0096352100372314, 3.470649003982544, 3.0710983276367188, 3.3230831623077393, 2.5442917346954346, 2.0903425216674805, 2.194819927215576, 2.2812986373901367, 2.534407377243042, 1.5441094636917114, 2.3895351886749268, 3.784731864929199, 2.8000099658966064, 3.269717216491699, 2.685222625732422, 3.1160991191864014, 3.319068431854248, 3.6023740768432617, 2.6993536949157715, 2.529099464416504, 1.9759576320648193, 2.3567821979522705, 1.6512188911437988, 1.9982043504714966, 4.198288440704346, 2.922656774520874, 1.6671628952026367, 2.167189598083496, 2.272754430770874, 2.8759877681732178, 2.4563684463500977, 4.003395080566406, 2.181811571121216, 3.0752594470977783, 1.7192623615264893, 1.9941095113754272, 1.5663505792617798, 2.439906597137451, 1.8883445262908936, 1.999293327331543, 3.58864426612854, 3.1605165004730225, 2.367180824279785, 2.6364049911499023, 1.9210175275802612, 3.4621167182922363, 3.113419771194458, 2.129462242126465, 1.7376106977462769, 1.2648156881332397, 2.900494337081909, 1.426274061203003, 1.8359283208847046, 1.992939829826355, 2.440631628036499, 2.8660640716552734, 2.757533550262451, 2.2220277786254883, 2.644129991531372, 1.8746803998947144, 3.037843942642212, 3.2033584117889404, 2.1414594650268555, 2.9717860221862793, 3.2685749530792236, 3.2607548236846924, 2.4393134117126465, 3.1302216053009033, 2.801030397415161, 3.1120598316192627, 3.493565559387207, 1.930037498474121, 2.420895576477051, 3.2906579971313477, 3.672337532043457, 3.8326616287231445, 3.1026203632354736, 2.9681453704833984, 2.907212495803833, 3.1645922660827637, 2.1044015884399414, 2.3019189834594727, 2.151461601257324, 2.0458571910858154, 2.6958606243133545, 1.48493492603302, 1.2701045274734497, 1.9857265949249268, 2.1556310653686523, 2.993731737136841, 2.0790956020355225, 2.5671794414520264, 2.6856677532196045, 2.86614990234375, 1.8492193222045898, 1.845237135887146, 2.9265522956848145, 2.7697741985321045, 2.1322357654571533, 4.355404376983643, 2.7833645343780518, 2.9193508625030518, 2.558150053024292, 2.337185859680176, 2.2472524642944336, 2.2368040084838867, 1.5140790939331055, 2.6320652961730957, 2.9344334602355957, 1.6619187593460083, 1.6235690116882324, 2.090540647506714, 2.5741777420043945, 2.8936493396759033, 1.7601728439331055, 2.9979710578918457, 2.2218449115753174, 3.3427820205688477, 3.247971773147583, 1.6109055280685425, 2.63785457611084, 2.14483904838562, 1.8286771774291992, 2.638840913772583, 3.3263347148895264, 2.626662492752075, 2.049757957458496, 2.97684383392334, 3.1128485202789307, 3.446110248565674, 3.3977043628692627, 2.3213586807250977, 2.3321168422698975, 2.4522805213928223, 1.588654637336731, 2.8097753524780273, 1.7906006574630737, 3.1106202602386475, 2.439554452896118, 3.4659814834594727, 2.915325164794922, 2.991445302963257, 2.547074317932129, 2.7501561641693115, 3.431033134460449, 2.3046672344207764, 3.4868414402008057, 3.3910515308380127, 2.9390552043914795, 2.513150215148926, 2.366504669189453, 2.471987724304199, 2.9007580280303955, 3.267716646194458, 2.2377004623413086, 2.708752393722534, 3.2724809646606445, 3.002453565597534, 3.5926504135131836, 3.012340545654297, 1.730015516281128, 2.0936803817749023, 2.2516183853149414, 2.414038896560669, 3.4284753799438477, 2.4685428142547607, 2.4482948780059814, 3.9233365058898926, 1.5145368576049805, 2.806985378265381, 3.0660998821258545, 2.161149024963379, 1.776713490486145, 2.4973506927490234, 3.906514883041382, 2.612805128097534, 3.7825212478637695, 2.1723203659057617, 1.963875651359558, 3.6474177837371826, 3.4072892665863037, 2.008826494216919, 2.5924084186553955, 2.0380756855010986, 2.4969916343688965, 2.686924934387207, 2.1574435234069824, 2.2387678623199463, 2.2256526947021484, 2.325474739074707, 3.173255205154419, 1.9504095315933228, 1.8178080320358276, 2.004117727279663, 2.7704460620880127, 2.4613771438598633, 2.866708278656006, 1.616713523864746, 2.8267107009887695, 1.5687443017959595, 2.198115587234497, 3.4134111404418945, 3.3651745319366455, 3.057202100753784, 3.6548051834106445, 1.9739456176757812, 4.402437210083008, 2.102778196334839, 2.778874397277832, 2.6218042373657227, 3.7386655807495117, 3.460726261138916, 3.3271396160125732, 3.4154253005981445, 2.3810744285583496, 2.865311861038208, 1.4214582443237305, 2.873244524002075, 3.654045820236206, 2.7926571369171143, 2.791813373565674, 1.9432156085968018, 2.784562349319458, 2.892521858215332, 3.4374840259552, 1.6362961530685425, 1.6399946212768555, 2.8380916118621826, 2.013378143310547, 3.008134126663208, 2.0040066242218018, 1.7366466522216797, 3.20927357673645, 2.317988872528076, 3.249814987182617, 2.534550666809082, 3.0405187606811523, 2.61850643157959, 2.9928812980651855, 0.2660188674926758, 0.21808913350105286, 0.23594427108764648, 0.2343101054430008, 0.18501244485378265, 0.22653640806674957, 0.2831532061100006, 0.29586178064346313, 0.2706691026687622, 0.22037746012210846, 0.2546065151691437, 0.19382353127002716, 0.2765205204486847, 0.18595847487449646, 0.22806651890277863, 0.2081521898508072, 0.28113794326782227, 0.2714134454727173, 0.2131451815366745, 0.21892836689949036, 0.2063356339931488, 0.27629509568214417, 0.2298998385667801, 0.24641521275043488, 0.19721205532550812, 0.23946599662303925, 0.23631279170513153, 0.2855926752090454, 0.21515540778636932, 0.21968284249305725, 0.27879443764686584, 0.27460211515426636, 0.22555296123027802, 0.27582451701164246, 0.2997876703739166, 0.24038605391979218, 0.20541296899318695, 0.2794845998287201, 0.23477207124233246, 0.2362854778766632, 0.217974454164505, 0.23423849046230316, 0.24244527518749237, 0.2242884337902069, 0.2466696947813034, 0.25351178646087646, 0.22051194310188293, 0.2709619104862213, 0.23495067656040192, 0.275383323431015, 0.2658442556858063, 0.27830708026885986, 0.26882055401802063, 0.21018695831298828, 0.21606408059597015, 0.21166273951530457, 0.22617390751838684, 0.1867404729127884, 0.28744348883628845, 0.21772325038909912, 0.22221523523330688, 0.22135967016220093, 0.29164424538612366, 0.2018059939146042, 0.2518342435359955, 0.23642203211784363, 0.19158652424812317, 0.24258235096931458, 0.22537697851657867, 0.2030082643032074, 0.23559778928756714, 0.232690691947937, 0.20491038262844086, 0.21934819221496582, 0.2636227607727051, 0.29655584692955017, 0.2357437014579773, 0.20684100687503815, 0.316811203956604, 0.2333858609199524, 0.26912352442741394, 0.3013584613800049, 0.22068631649017334, 0.21160808205604553, 0.23855185508728027, 0.23565877974033356, 0.1824176162481308, 0.28002649545669556, 0.2868744730949402, 0.31117314100265503, 0.24237750470638275, 0.22001229226589203, 0.25361737608909607, 0.22429871559143066, 0.24451231956481934, 0.21957099437713623, 0.2016730010509491, 0.3000803291797638, 0.22774527966976166, 0.2646563947200775, 0.2789534032344818, 0.3081118166446686, 0.2101343423128128, 0.30800458788871765, 0.24514153599739075, 0.22476635873317719, 0.3037899434566498, 0.19598640501499176, 0.23244479298591614, 0.2578192949295044, 0.31916192173957825, 0.18823184072971344, 0.24215877056121826, 0.28633832931518555, 0.2900111675262451, 0.2062564492225647, 0.27956947684288025, 0.2042776197195053, 0.23601099848747253, 0.2012709379196167, 0.21399711072444916, 0.24712339043617249, 0.2632285952568054, 0.1979118287563324, 0.2548929452896118, 0.164072647690773, 0.2532658576965332, 0.2242681235074997, 0.271355539560318, 0.20120185613632202, 0.22574374079704285, 0.2731195092201233, 0.20692861080169678, 0.23730701208114624, 0.21933209896087646, 0.22062678635120392, 0.2230081558227539, 0.19667382538318634, 0.21421824395656586, 0.20962586998939514, 0.2545482814311981, 0.22332485020160675, 0.2925826907157898, 0.3097398281097412, 0.1365000605583191, 0.28296205401420593, 0.2894499897956848, 0.2367427945137024, 0.2539849877357483, 0.2454715073108673, 0.1874728798866272, 0.23275427520275116, 0.2476842850446701, 0.20218425989151, 0.2924157977104187, 0.23818762600421906, 0.2338477075099945, 0.16934442520141602, 0.30190515518188477, 0.24334730207920074, 0.26779937744140625, 0.2438468188047409, 0.24684104323387146, 0.23468619585037231, 0.17321817576885223, 0.2700002193450928, 0.24611270427703857, 0.23769161105155945, 0.2504193186759949, 0.2376892864704132, 0.26450175046920776, 0.20416194200515747, 0.2966395914554596, 0.2937687933444977, 0.29171323776245117, 0.21646247804164886, 0.2787606418132782, 0.22334985435009003, 0.24321787059307098, 0.2360001653432846, 0.2380860149860382, 0.2448219656944275, 0.19165439903736115, 0.20839248597621918, 0.28662604093551636, 0.23076274991035461, 0.230899378657341, 0.2806302607059479, 0.19277961552143097, 0.15853558480739594, 0.19041287899017334, 0.18477946519851685, 0.2633485794067383, 0.2502845823764801, 0.22618623077869415, 0.1914600133895874, 0.2193632274866104, 0.20615580677986145, 0.2531331181526184, 0.19432632625102997, 0.22808977961540222, 0.230097696185112, 0.2983936369419098, 0.15882453322410583, 0.27328968048095703, 0.24888625741004944, 0.1792374700307846, 0.2404475212097168, 0.21590593457221985, 0.23434190452098846, 0.19323621690273285, 0.31893840432167053, 0.24095293879508972, 0.2050211876630783, 0.27456802129745483, 0.2656813859939575, 0.1943170577287674, 0.18223486840724945, 0.2845904231071472, 0.22865024209022522, 0.22179153561592102, 0.2920566201210022, 0.2609739601612091, 0.29616594314575195, 0.24165809154510498, 0.23703910410404205, 0.21150945127010345, 0.16920152306556702, 0.2671363055706024, 0.2737302780151367, 0.230706587433815, 0.18855725228786469, 0.26514363288879395, 0.18153269588947296, 0.2747521996498108, 0.22201667726039886, 0.2933555543422699, 0.30605757236480713, 0.281238317489624, 0.20925767719745636, 0.2620077133178711, 0.2060372531414032, 0.22069525718688965, 0.224001944065094, 0.23974230885505676, 0.2437087595462799, 0.2224942296743393, 0.21985571086406708, 0.2217443734407425, 0.19930139183998108, 0.22612369060516357, 0.2778632938861847, 0.23940536379814148, 0.19572345912456512, 0.2914474904537201, 0.225035160779953, 0.20808862149715424, 0.2027004361152649, 0.2767488360404968, 0.22640414535999298, 0.17969512939453125, 0.28009429574012756, 0.23777110874652863, 0.2632310092449188, 0.2093987762928009, 0.25690698623657227, 0.2087167501449585, 0.25835102796554565, 0.27146589756011963, 0.18400856852531433, 0.20142583549022675, 0.21261195838451385, 0.24871580302715302, 0.2153138369321823, 0.19613833725452423, 0.25715240836143494, 0.23045216500759125, 0.18320636451244354, 0.2122466266155243, 0.29107528924942017, 0.18780845403671265, 0.27260538935661316, 0.27016693353652954, 0.2639809250831604, 0.21610140800476074, 0.2131737470626831, 0.2570430040359497, 0.20283842086791992, 0.23549018800258636, 0.2559022009372711, 0.20408974587917328, 0.23033873736858368, 0.23228274285793304, 0.1722414791584015, 0.19016654789447784, 0.31859928369522095, 0.20617693662643433, 0.23147153854370117, 0.24866850674152374, 0.19481822848320007, 3.522057056427002, 5.644720554351807, 3.863844633102417, 2.329695463180542, 2.6076788902282715, 3.2990353107452393, 2.485806465148926, 3.0003039836883545, 1.8447670936584473, 3.8202943801879883, 3.549286365509033, 3.2520909309387207, 2.9182956218719482, 1.912121057510376, 3.112504243850708, 2.7050251960754395, 2.706249952316284, 3.200831413269043, 1.7850936651229858, 2.8204498291015625, 3.5307235717773438, 2.940311908721924, 3.332679033279419, 2.9021236896514893, 3.9000039100646973, 3.141576051712036, 3.8231418132781982, 2.583672523498535, 2.4305078983306885, 4.397223949432373, 2.5063700675964355, 3.933596611022949, 3.659235715866089, 3.81900691986084, 3.1676762104034424, 2.38265323638916, 3.033982515335083, 3.364903211593628, 4.174288272857666, 2.7471683025360107, 2.2379183769226074, 3.6606550216674805, 2.437985897064209, 4.265310287475586, 2.201080799102783, 2.781365394592285, 4.432949066162109, 3.8534436225891113, 3.168172836303711, 3.6454918384552, 3.232003927230835, 4.247053623199463, 3.8900070190429688, 2.477074146270752, 3.211726665496826, 3.9860165119171143, 3.3297195434570312, 4.989792823791504, 4.308110237121582, 1.7581672668457031, 2.905825138092041, 2.3699145317077637, 2.1217868328094482, 1.8797575235366821, 2.6150712966918945, 3.131484270095825, 3.7845962047576904, 3.267503023147583, 2.32930326461792, 3.854353904724121, 3.311038017272949, 3.2969272136688232, 3.3039321899414062, 3.5987942218780518, 1.961545705795288, 4.897153377532959, 2.666630506515503, 3.097562074661255, 2.972623109817505, 3.2542965412139893, 2.425238847732544, 4.024537086486816, 3.226182222366333, 2.2439424991607666, 2.9760327339172363, 2.9975316524505615, 3.3890132904052734, 4.111579895019531, 2.832634449005127, 3.520505905151367, 3.1237072944641113, 3.524858236312866, 2.570720672607422, 2.5648193359375, 3.397770881652832, 3.46684193611145, 3.0825436115264893, 4.372072696685791, 3.522137403488159, 2.8828837871551514, 1.7514230012893677, 1.754969596862793, 2.194957971572876, 3.8089451789855957, 2.5709424018859863, 3.182976245880127, 2.8880462646484375, 2.9270341396331787, 3.762761354446411, 3.6107945442199707, 2.1004300117492676, 4.223409652709961, 3.7749862670898438, 2.3661203384399414, 2.6069207191467285, 2.950697660446167, 2.83549165725708, 3.4406750202178955, 2.863295316696167, 4.163054943084717, 3.268496513366699, 4.338990688323975, 3.432072639465332, 2.941692352294922, 3.8654003143310547, 4.421339511871338, 3.0896224975585938, 2.107733726501465, 2.838761568069458, 2.792250394821167, 2.582216739654541, 2.2252213954925537, 3.239483594894409, 1.661293864250183, 3.1000277996063232, 2.778210401535034, 2.7157671451568604, 2.28023624420166, 3.709280252456665, 2.574087142944336, 1.9775058031082153, 4.574300289154053, 4.820679187774658, 3.0225284099578857, 3.3665263652801514, 2.6296050548553467, 3.557772159576416, 4.087801456451416, 3.525599956512451, 2.2629692554473877, 3.2015533447265625, 2.0024983882904053, 2.941058397293091, 2.4491662979125977, 3.354421615600586, 3.6732559204101562, 3.533297538757324, 3.266788959503174, 3.731473207473755, 3.048684597015381, 1.6737418174743652, 2.7249231338500977, 2.8107409477233887, 4.050034046173096, 3.7551159858703613, 2.7719273567199707, 2.3820974826812744, 2.2306501865386963, 3.0064709186553955, 2.982788562774658, 2.7771198749542236, 2.58807373046875, 2.0372154712677, 2.798567533493042, 4.334539890289307, 2.9407875537872314, 3.1079914569854736, 2.753042459487915, 4.61698055267334, 2.9187042713165283, 3.3619298934936523, 2.056595802307129, 2.383229970932007, 3.0170178413391113, 2.875708818435669, 3.405820846557617, 2.646972179412842, 2.7540974617004395, 3.8457717895507812, 1.6724929809570312, 3.091431140899658, 1.4871584177017212, 2.8007519245147705, 4.106411457061768, 2.593909740447998, 3.4248533248901367, 5.210225582122803, 2.7012298107147217, 3.057896614074707, 2.2236852645874023, 3.2468886375427246, 3.158951997756958, 3.7481677532196045, 3.1430656909942627, 3.4555022716522217, 3.0991909503936768, 3.345451831817627, 3.427354574203491, 3.0190234184265137, 2.731130838394165, 3.2447032928466797, 3.368098735809326, 2.6598057746887207, 1.769930362701416, 2.467832565307617, 2.8744163513183594, 2.7705142498016357, 3.5994648933410645, 2.0220260620117188, 3.737415075302124, 2.6874477863311768, 4.068393230438232, 2.0925686359405518, 2.733222484588623, 3.574544906616211, 4.777843952178955, 2.2132606506347656, 2.8976669311523438, 1.861918330192566, 3.759397506713867, 2.903229236602783, 4.248753547668457, 2.845921277999878, 2.5908775329589844, 3.943800210952759, 2.4771525859832764, 2.7341930866241455, 3.1319198608398438, 2.7020504474639893, 2.20218563079834, 1.955863118171692, 3.029726505279541, 4.262655735015869, 1.9551934003829956, 3.4025726318359375, 3.7870118618011475, 2.36130952835083, 3.3019204139709473, 2.138303279876709, 3.6433446407318115, 3.3494186401367188, 2.4382481575012207, 2.4541754722595215, 3.0326473712921143, 3.281287431716919, 3.312166690826416, 3.028447389602661, 2.5564651489257812, 1.994803786277771, 2.3171401023864746, 2.7289628982543945, 3.322516441345215, 2.4987215995788574, 2.6251988410949707, 3.8084514141082764, 4.429383277893066, 2.349332332611084, 2.943824052810669, 2.3278818130493164, 3.4528207778930664, 2.400355815887451, 2.317495584487915, 2.4076247215270996, 2.801954984664917, 2.4611339569091797, 2.585458517074585, 3.0870697498321533, 2.350339889526367, 3.4980709552764893, 2.2438061237335205, 3.0238888263702393, 3.0999248027801514, 3.5203518867492676, 2.4344382286071777, 2.30764102935791, 4.073354721069336, 2.3913779258728027, 2.1204233169555664, 2.6350252628326416, 2.349471092224121, 2.7344982624053955, 2.079702138900757, 3.9471404552459717, 2.6793293952941895, 3.3859050273895264, 2.188171863555908, 3.4235451221466064, 2.3652496337890625, 3.1531312465667725, 3.332811117172241, 470.31378173828125, 171.39340209960938, 132.87673950195312, 73.16205596923828, 381.2987365722656, 104.60021209716797, 446.0994567871094, 239.8284912109375, 230.5634307861328, 84.95833587646484, 96.9305648803711, 267.47857666015625, 184.20175170898438, 324.630615234375, 315.8468017578125, 336.21044921875, 273.02117919921875, 73.51150512695312, 155.8915252685547, 43.3509521484375, 317.6037902832031, 253.16262817382812, 244.31805419921875, 61.70361328125, 239.1390380859375, 397.4969787597656, 152.15711975097656, 62.10009765625, 193.072021484375, 628.596923828125, 81.60944366455078, 153.27850341796875, 221.54551696777344, 135.7955780029297, 120.19107055664062, 496.3704528808594, 62.850364685058594, 266.447998046875, 106.16849517822266, 206.7133331298828, 409.6009521484375, 261.8154296875, 193.4305419921875, 314.0972900390625, 374.6983947753906, 133.75927734375, 57.75699234008789, 360.7498474121094, 242.99961853027344, 101.02945709228516, 338.89208984375, 58.598445892333984, 450.793701171875, 192.12026977539062, 44.97332763671875, 323.8115234375, 92.0477294921875, 361.6668701171875, 141.89646911621094, 135.79063415527344, 262.59075927734375, 287.532958984375, 313.88812255859375, 329.56146240234375, 206.0755615234375, 366.787841796875, 298.48931884765625, 103.44928741455078, 176.62725830078125, 162.5511932373047, 195.2694091796875, 301.794677734375, 176.1354522705078, 383.0396728515625, 423.429443359375, 383.5252380371094, 224.4882049560547, 418.0187072753906, 198.7060546875, 274.1595458984375, 197.95079040527344, 334.2645568847656, 254.38037109375, 70.58932495117188, 43.135623931884766, 139.80860900878906, 210.86253356933594, 90.416015625, 95.28170013427734, 168.6136474609375, 548.658203125, 132.11798095703125, 323.16650390625, 103.29630279541016, 461.7864074707031, 417.1888427734375, 147.04806518554688, 96.69110107421875, 138.15435791015625, 55.70844650268555, 154.23562622070312, 418.2970886230469, 608.5905151367188, 228.17205810546875, 459.1195068359375, 296.4095153808594, 173.92913818359375, 196.7504119873047, 289.91119384765625, 80.84440612792969, 528.0184936523438, 221.3406524658203, 87.17474365234375, 352.97235107421875, 143.77059936523438, 453.2613525390625, 445.6846923828125, 124.9368896484375, 696.7037353515625, 134.7265625, 113.3416976928711, 360.8299255371094, 109.33204650878906, 91.34259796142578, 278.7377014160156, 244.1946258544922, 97.39111328125, 63.9254150390625, 105.98641204833984, 331.0872497558594, 492.24908447265625, 368.3302917480469, 164.93104553222656, 171.6390380859375, 439.1818542480469, 411.7015380859375, 177.2501983642578, 253.07449340820312, 264.99188232421875, 382.7579650878906, 361.581787109375, 148.18771362304688, 79.25405883789062, 260.29345703125, 254.4928436279297, 231.21592712402344, 226.20233154296875, 205.91751098632812, 79.12409210205078, 157.468505859375, 119.61592864990234, 196.9472198486328, 117.67792510986328, 335.06085205078125, 377.5425720214844, 50.5521240234375, 381.2455139160156, 62.96657943725586, 147.82568359375, 205.88389587402344, 172.06784057617188, 346.8165588378906, 82.4058609008789, 336.42279052734375, 142.7631072998047, 397.7102966308594, 49.16775131225586, 43.3128662109375, 385.4393615722656, 251.5107421875, 416.88214111328125, 100.97750091552734, 98.45226287841797, 400.2762756347656, 174.16195678710938, 87.62353515625, 186.9787139892578, 71.02516174316406, 242.3471221923828, 248.1826171875, 306.8743591308594, 291.1314697265625, 60.738792419433594, 507.54937744140625, 326.4052734375, 235.84288024902344, 253.57058715820312, 297.6565856933594, 286.33270263671875, 352.0347595214844, 313.3726806640625, 689.1687622070312, 43.5701904296875, 68.16189575195312, 271.77313232421875, 239.29852294921875, 206.10687255859375, 310.7601013183594, 269.9266052246094, 175.7537841796875, 153.2311248779297, 103.35065460205078, 224.82925415039062, 444.0177307128906, 227.95999145507812, 214.9549102783203, 233.40147399902344, 518.682373046875, 134.439697265625, 250.56678771972656, 338.45770263671875, 100.75650024414062, 488.8251037597656, 169.85960388183594, 304.2376403808594, 241.44757080078125, 92.44720458984375, 80.3668212890625, 472.0859375, 165.7195281982422, 92.84357452392578, 211.4970703125, 42.453670501708984, 425.3927917480469, 253.9983367919922, 112.826171875, 176.013671875, 191.07882690429688, 188.9224395751953, 168.06671142578125, 211.916015625, 57.26414108276367, 185.4906005859375, 134.96055603027344, 52.28249740600586, 345.0289001464844, 267.0951843261719, 152.98056030273438, 237.1814727783203, 342.0329284667969, 468.0148010253906, 318.2325439453125, 174.373046875, 136.203857421875, 147.54513549804688, 279.53125, 178.58351135253906, 403.7501525878906, 73.86045837402344, 261.8615417480469, 199.8427734375, 169.31103515625, 70.71612548828125, 675.263427734375, 179.9429473876953, 119.87511444091797, 144.51719665527344, 589.245849609375, 186.717529296875, 346.19146728515625, 329.5509948730469, 323.25506591796875, 231.8319854736328, 160.94970703125, 221.4964599609375, 205.920654296875, 482.6407775878906, 522.041259765625, 356.6421813964844, 146.0196075439453, 163.021728515625, 192.58642578125, 203.1552734375, 202.0106201171875, 104.84302520751953, 489.49951171875, 342.132568359375, 382.1282653808594, 140.2567138671875, 288.3810729980469, 48.584228515625, 214.10617065429688, 329.7680358886719, 59.52930450439453, 59.648651123046875, 430.1889343261719, 307.69873046875, 281.0517578125, 187.2635498046875, 341.4127197265625, 337.2529602050781, 86.09679412841797, 131.13134765625, 193.8885040283203, 258.1394958496094, 188.33421325683594, 353.30023193359375, 218.654296875, 124.14112854003906, 369.2240295410156, 2.3726303577423096, 2.8924930095672607, 3.6237576007843018, 2.694751024246216, 2.7779808044433594, 4.0120415687561035, 3.801429033279419, 2.536261558532715, 4.260628700256348, 2.665532112121582, 2.649946928024292, 2.6527230739593506, 1.3671441078186035, 2.2954416275024414, 2.734429359436035, 3.842888593673706, 2.3284523487091064, 2.462141752243042, 3.5626652240753174, 3.0043864250183105, 2.719378709793091, 3.427037239074707, 2.681425094604492, 3.159069776535034, 2.0320959091186523, 3.067849636077881, 3.704246997833252, 1.922921061515808, 2.8534996509552, 1.8199529647827148, 3.2161929607391357, 4.245976448059082, 2.90374493598938, 3.981438398361206, 2.331846237182617, 2.6909613609313965, 2.9354641437530518, 2.6434850692749023, 3.56205677986145, 3.0541794300079346, 2.3431100845336914, 3.4534568786621094, 2.2340192794799805, 2.2524466514587402, 2.2219531536102295, 2.645568370819092, 2.0624706745147705, 2.2115347385406494, 2.098958730697632, 3.596083879470825, 2.1169214248657227, 3.321072816848755, 3.8011157512664795, 2.804821729660034, 3.684941291809082, 2.9610631465911865, 3.2120769023895264, 3.0131351947784424, 2.2152678966522217, 1.4204663038253784, 3.099285125732422, 2.9520530700683594, 2.508681297302246, 3.6864559650421143, 2.049161672592163, 2.1947431564331055, 3.751617908477783, 1.9173504114151, 2.6727728843688965, 2.6375465393066406, 3.3035290241241455, 2.416370153427124, 2.403745412826538, 2.5808823108673096, 1.7988206148147583, 3.4049413204193115, 2.134356737136841, 2.3088388442993164, 2.8433749675750732, 2.368858575820923, 3.588251829147339, 2.744702100753784, 2.601794958114624, 2.753535747528076, 1.5865375995635986, 2.698389768600464, 1.409485936164856, 3.488990068435669, 3.10491943359375, 3.4922420978546143, 2.6913554668426514, 3.167356491088867, 2.8390915393829346, 2.620896577835083, 1.9272842407226562, 1.9254796504974365, 3.7407078742980957, 3.203303098678589, 1.6619901657104492, 3.1361358165740967, 2.2874083518981934, 2.487258195877075, 3.374375581741333, 1.8852320909500122, 3.052415132522583, 2.9207088947296143, 3.298604726791382, 2.4393186569213867, 1.6861028671264648, 1.6781911849975586, 2.996089220046997, 2.880784511566162, 2.7295773029327393, 1.7965378761291504, 2.989557981491089, 2.400648832321167, 3.125971555709839, 2.534425973892212, 2.2885522842407227, 2.162137031555176, 2.344256639480591, 3.1409497261047363, 1.9133423566818237, 2.757688045501709, 4.056976318359375, 2.843397855758667, 3.0052928924560547, 2.6167654991149902, 3.5084826946258545, 2.988123655319214, 1.9248006343841553, 2.3001832962036133, 3.248420238494873, 2.2490592002868652, 2.313690185546875, 2.1881988048553467, 2.844696044921875, 1.4783248901367188, 2.7768123149871826, 3.388108491897583, 2.212956428527832, 2.5980327129364014, 2.3505547046661377, 2.8333940505981445, 2.3940281867980957, 2.374528646469116, 2.033139228820801, 2.248805046081543, 2.071969509124756, 2.2841196060180664, 3.0233566761016846, 2.20371150970459, 2.93395733833313, 2.9237091541290283, 3.2203569412231445, 3.1906957626342773, 2.909716844558716, 1.9020557403564453, 2.664219856262207, 3.0013999938964844, 3.4786217212677, 2.207535743713379, 3.4133787155151367, 1.5702446699142456, 3.51222825050354, 2.6472625732421875, 1.287657618522644, 3.5384092330932617, 3.073960542678833, 2.7475831508636475, 3.87152099609375, 3.877631187438965, 2.654444456100464, 1.6479653120040894, 2.79287052154541, 3.0964577198028564, 1.9611173868179321, 3.564297914505005, 3.2116382122039795, 3.4545257091522217, 2.46734619140625, 2.0267746448516846, 2.343916893005371, 2.5180554389953613, 1.8929146528244019, 1.9787262678146362, 3.5254170894622803, 3.1007626056671143, 3.070716142654419, 2.0339574813842773, 2.1744325160980225, 3.099616289138794, 3.1774327754974365, 2.573260545730591, 3.2900876998901367, 3.345187187194824, 2.241673469543457, 2.7515172958374023, 2.451125144958496, 2.651695728302002, 3.50146222114563, 2.6090087890625, 3.134774684906006, 2.7967944145202637, 2.4526891708374023, 2.3566808700561523, 1.9301671981811523, 3.0397884845733643, 2.8320956230163574, 1.6261430978775024, 1.8803414106369019, 3.084200382232666, 1.2951592206954956, 2.298699378967285, 2.7549548149108887, 2.264681339263916, 2.5584359169006348, 3.268873453140259, 2.6086950302124023, 3.180776357650757, 2.63543701171875, 2.6214892864227295, 2.7162458896636963, 2.0455446243286133, 2.0156641006469727, 2.2680869102478027, 3.012479066848755, 4.5255327224731445, 3.610316276550293, 2.4708354473114014, 2.5470263957977295, 2.464595079421997, 2.7490246295928955, 2.448004722595215, 2.6194357872009277, 2.6237077713012695, 2.4860620498657227, 2.5387463569641113, 1.5128496885299683, 3.702181816101074, 3.4553134441375732, 1.7468109130859375, 3.4942402839660645, 3.8051977157592773, 3.8407719135284424, 3.4080498218536377, 2.4262285232543945, 2.7288742065429688, 2.8319218158721924, 2.045398473739624, 1.7280510663986206, 1.9901747703552246, 2.5199649333953857, 2.878416061401367, 2.0490808486938477, 3.0366897583007812, 1.2032231092453003, 2.9155187606811523, 3.832362174987793, 3.5605669021606445, 2.031869411468506, 2.466787338256836, 2.6902170181274414, 2.485234260559082, 3.3568413257598877, 2.4685068130493164, 2.6773064136505127, 2.328904151916504, 3.8513882160186768, 3.0385961532592773, 1.7553664445877075, 2.3552064895629883, 3.7658474445343018, 2.0708508491516113, 1.7313576936721802, 2.5513792037963867, 2.4463858604431152, 2.7935991287231445, 2.7294511795043945, 2.88625431060791, 2.753971576690674, 2.193556785583496, 1.8325834274291992, 2.8632421493530273, 1.9400032758712769, 4.1389546394348145, 1.6895076036453247, 2.8256242275238037, 2.0204896926879883, 3.2200138568878174, 2.9563915729522705, 2.08402943611145, 2.7008960247039795, 1.1580604314804077, 2.877577781677246, 1.8526743650436401, 3.2521443367004395, 2.7733240127563477, 3.165900468826294, 2.9534313678741455, 0.31008338928222656, 0.21560512483119965, 0.28006860613822937, 0.19957025349140167, 0.30244117975234985, 0.2015114575624466, 0.27819401025772095, 0.23585200309753418, 0.1993304044008255, 0.28654035925865173, 0.2696043848991394, 0.22271139919757843, 0.2320805937051773, 0.21300874650478363, 0.2359059900045395, 0.2642524540424347, 0.21397042274475098, 0.2637023627758026, 0.19273240864276886, 0.22615844011306763, 0.3010215759277344, 0.25304874777793884, 0.24985657632350922, 0.30250048637390137, 0.20933979749679565, 0.26187729835510254, 0.1915714293718338, 0.29696160554885864, 0.2798963785171509, 0.19747257232666016, 0.1685791015625, 0.25217124819755554, 0.33408239483833313, 0.22011883556842804, 0.2536872923374176, 0.201878622174263, 0.2692214846611023, 0.30173391103744507, 0.21969306468963623, 0.26640650629997253, 0.24071381986141205, 0.24997299909591675, 0.2920856475830078, 0.23468531668186188, 0.22258174419403076, 0.2590869665145874, 0.29773610830307007, 0.27618318796157837, 0.22113633155822754, 0.33155685663223267, 0.2768341600894928, 0.2725640535354614, 0.2709364891052246, 0.25231802463531494, 0.3071805238723755, 0.27592575550079346, 0.25091660022735596, 0.14665591716766357, 0.30614298582077026, 0.27273571491241455, 0.2570755183696747, 0.2640368342399597, 0.22544319927692413, 0.2961968779563904, 0.24116134643554688, 0.22800488770008087, 0.24971573054790497, 0.20006869733333588, 0.2614020109176636, 0.22068865597248077, 0.2077750712633133, 0.2961680293083191, 0.2447178214788437, 0.21798095107078552, 0.28021755814552307, 0.20707178115844727, 0.26179206371307373, 0.26343679428100586, 0.26079061627388, 0.22794201970100403, 0.2824176251888275, 0.23693333566188812, 0.2637529671192169, 0.26920250058174133, 0.20456205308437347, 0.22289705276489258, 0.2357577532529831, 0.2645888328552246, 0.17513445019721985, 0.2625197768211365, 0.24450883269309998, 0.2665683627128601, 0.21893011033535004, 0.16376210749149323, 0.2999195456504822, 0.2195805311203003, 0.23373344540596008, 0.2709444463253021, 0.30598530173301697, 0.2525148391723633, 0.17493820190429688, 0.26291611790657043, 0.3074020445346832, 0.2940419018268585, 0.2368488311767578, 0.16305366158485413, 0.24844898283481598, 0.2690916955471039, 0.16759811341762543, 0.246200293302536, 0.2364126741886139, 0.21965621411800385, 0.25969359278678894, 0.23545905947685242, 0.27428773045539856, 0.20463714003562927, 0.25046825408935547, 0.26513391733169556, 0.24181202054023743, 0.22261832654476166, 0.3028249740600586, 0.19058045744895935, 0.24975313246250153, 0.22185450792312622, 0.24464945495128632, 0.2262146919965744, 0.30630260705947876, 0.2059543877840042, 0.2611788809299469, 0.19528895616531372, 0.2241065949201584, 0.22529098391532898, 0.24881550669670105, 0.2621496021747589, 0.22392985224723816, 0.283221036195755, 0.26445555686950684, 0.27861663699150085, 0.28868335485458374, 0.2930840253829956, 0.23722942173480988, 0.2561747133731842, 0.20904363691806793, 0.19890281558036804, 0.2222936898469925, 0.24966154992580414, 0.22724051773548126, 0.2514550983905792, 0.28174570202827454, 0.26404863595962524, 0.24273188412189484, 0.2604312598705292, 0.22283607721328735, 0.17409661412239075, 0.24825069308280945, 0.2704037129878998, 0.3173966407775879, 0.24519065022468567, 0.2327326089143753, 0.2717689275741577, 0.2462833970785141, 0.22747580707073212, 0.3187585473060608, 0.21488673985004425, 0.22245906293392181, 0.244968444108963, 0.3400737941265106, 0.26266714930534363, 0.31156349182128906, 0.24247434735298157, 0.1925489455461502, 0.31649479269981384, 0.31832355260849, 0.2580382823944092, 0.17691634595394135, 0.2587488889694214, 0.19932964444160461, 0.20134790241718292, 0.1926392763853073, 0.25264155864715576, 0.25933095812797546, 0.2559821307659149, 0.26351305842399597, 0.17468459904193878, 0.20322053134441376, 0.22011971473693848, 0.2764624357223511, 0.28710830211639404, 0.242120161652565, 0.21334397792816162, 0.2453550100326538, 0.26456376910209656, 0.259899377822876, 0.23906484246253967, 0.26695990562438965, 0.2192995399236679, 0.24758368730545044, 0.2138143628835678, 0.31162646412849426, 0.16597695648670197, 0.2735404670238495, 0.21393771469593048, 0.2478996068239212, 0.25648558139801025, 0.21585379540920258, 0.2048020362854004, 0.28418734669685364, 0.2846784293651581, 0.24851985275745392, 0.259616494178772, 0.2601219117641449, 0.1767236441373825, 0.24911826848983765, 0.21074575185775757, 0.2320447713136673, 0.24149353802204132, 0.24694307148456573, 0.2597728967666626, 0.23638980090618134, 0.19377779960632324, 0.21732844412326813, 0.24142546951770782, 0.24831126630306244, 0.2912481129169464, 0.20856669545173645, 0.2616094648838043, 0.21835662424564362, 0.25634700059890747, 0.284131795167923, 0.2399638444185257, 0.24244077503681183, 0.22280772030353546, 0.21841862797737122, 0.2530769407749176, 0.2949608266353607, 0.24276931583881378, 0.28947845101356506, 0.22818055748939514, 0.1966208964586258, 0.281305193901062, 0.22291582822799683, 0.2238422930240631, 0.3178912103176117, 0.2567797899246216, 0.2777312695980072, 0.22980472445487976, 0.25019145011901855, 0.21726371347904205, 0.21312999725341797, 0.2706040143966675, 0.18524062633514404, 0.2681233286857605, 0.27237018942832947, 0.18953247368335724, 0.3087417781352997, 0.2525988817214966, 0.23049962520599365, 0.2704601287841797, 0.28963980078697205, 0.25177136063575745, 0.23750098049640656, 0.2316395491361618, 0.2322397232055664, 0.21176795661449432, 0.2244826704263687, 0.2038988322019577, 0.2165878266096115, 0.25155481696128845, 0.27829235792160034, 0.24464665353298187, 0.246474489569664, 0.2867475748062134, 0.22386839985847473, 0.21181367337703705, 0.3021240532398224, 0.28428933024406433, 0.20657557249069214, 0.2412807047367096, 0.3109825849533081, 0.27401894330978394, 0.2886428236961365, 0.24665331840515137, 0.3023936450481415, 0.2535148561000824, 0.23166175186634064, 0.2574881613254547, 0.2875335216522217, 0.23064088821411133, 0.3063342869281769, 0.2915259003639221, 0.2298465073108673, 0.23695163428783417, 0.21440990269184113, 0.22306214272975922, 0.21550075709819794, 0.2683982253074646, 0.2885107100009918, 0.23090051114559174, 0.19520075619220734, 0.29348453879356384, 3.4651882648468018, 3.1254048347473145, 4.1884894371032715, 2.5221757888793945, 1.7352455854415894, 3.387681722640991, 3.8211910724639893, 4.216802597045898, 2.4689626693725586, 3.034564733505249, 3.0481274127960205, 3.499667167663574, 2.106149435043335, 5.143312931060791, 3.1620616912841797, 1.9686208963394165, 2.015014410018921, 2.8887898921966553, 3.334881544113159, 3.5168533325195312, 3.4900200366973877, 3.716756820678711, 4.309535980224609, 2.281374216079712, 5.323365211486816, 4.2851128578186035, 3.250770092010498, 3.5203468799591064, 3.7240841388702393, 3.1451175212860107, 3.9589428901672363, 3.4969663619995117, 3.544499397277832, 2.5727639198303223, 3.9843406677246094, 2.5341708660125732, 2.3299388885498047, 2.4831454753875732, 3.081362247467041, 2.9644055366516113, 3.385869264602661, 3.7122180461883545, 2.078716516494751, 4.1567230224609375, 2.2169876098632812, 2.803204298019409, 2.056112289428711, 2.297637701034546, 1.8146542310714722, 4.093501091003418, 2.154317617416382, 1.8897452354431152, 2.074690580368042, 3.486647605895996, 3.211346387863159, 3.114823579788208, 3.1697258949279785, 3.7012574672698975, 2.6714677810668945, 2.362575054168701, 3.663835287094116, 4.333473205566406, 3.849879741668701, 3.8689563274383545, 2.512777090072632, 2.6259496212005615, 3.498652219772339, 3.3128232955932617, 2.478943347930908, 3.6743931770324707, 4.274510383605957, 4.01663875579834, 2.355152130126953, 3.5343663692474365, 1.999058485031128, 3.287682056427002, 2.2830331325531006, 2.1182479858398438, 2.2816810607910156, 2.5015182495117188, 3.204624891281128, 2.046664237976074, 3.201721668243408, 2.2516489028930664, 2.976736068725586, 2.2458291053771973, 2.733891010284424, 2.9739842414855957, 3.2952489852905273, 2.4373388290405273, 3.988591432571411, 2.6043624877929688, 3.352872610092163, 2.6138129234313965, 2.921657085418701, 2.8531405925750732, 2.3324830532073975, 4.070281505584717, 2.084228515625, 2.8183529376983643, 2.145969867706299, 3.1324450969696045, 2.4508235454559326, 2.3190910816192627, 3.7082042694091797, 1.8398628234863281, 2.4133400917053223, 2.9839909076690674, 3.599966049194336, 4.058894157409668, 1.9526846408843994, 2.7935943603515625, 2.0544328689575195, 2.1963016986846924, 2.324049234390259, 2.13558292388916, 2.7361843585968018, 2.1356117725372314, 2.1120734214782715, 4.093523025512695, 2.8148791790008545, 2.3166308403015137, 2.841068744659424, 3.0799999237060547, 3.8621788024902344, 2.4941515922546387, 3.2931110858917236, 2.3980612754821777, 2.7479348182678223, 3.028905153274536, 2.387068748474121, 3.374620199203491, 3.5863773822784424, 2.9246978759765625, 2.8780784606933594, 3.2452168464660645, 2.784555196762085, 3.2245700359344482, 3.5746753215789795, 2.7811906337738037, 2.2262792587280273, 3.9323482513427734, 3.2899694442749023, 2.965289831161499, 3.098386764526367, 4.542497634887695, 2.856736898422241, 3.3615074157714844, 2.1699423789978027, 2.1033341884613037, 3.3542113304138184, 3.979600667953491, 3.2500951290130615, 2.962772846221924, 4.516942024230957, 2.7675247192382812, 3.1146929264068604, 2.416463851928711, 2.5216760635375977, 3.1139988899230957, 3.3971779346466064, 3.8612563610076904, 1.9544175863265991, 3.289304733276367, 2.3852310180664062, 2.1270833015441895, 3.2870540618896484, 4.207314968109131, 2.894890785217285, 3.4868035316467285, 3.1595635414123535, 3.2660140991210938, 2.2235305309295654, 3.9251708984375, 2.199843168258667, 1.8590407371520996, 2.1578826904296875, 3.551459550857544, 3.488255739212036, 3.8362953662872314, 2.0947980880737305, 3.6179263591766357, 2.8559460639953613, 3.3447039127349854, 3.1541714668273926, 3.105572462081909, 2.4785988330841064, 2.2927870750427246, 4.636910438537598, 1.9204133749008179, 2.1040472984313965, 3.9999804496765137, 2.6775169372558594, 3.2782115936279297, 2.2574827671051025, 2.053847312927246, 3.415698766708374, 3.4886436462402344, 3.2543821334838867, 2.5818822383880615, 3.637986421585083, 2.375922441482544, 2.2993247509002686, 2.7410545349121094, 2.0511457920074463, 2.7779839038848877, 4.55037260055542, 1.7592735290527344, 3.3937041759490967, 3.1752662658691406, 2.2546682357788086, 3.3670802116394043, 2.4281716346740723, 2.893357515335083, 3.70544171333313, 3.4346020221710205, 3.6377246379852295, 2.904498338699341, 2.434448480606079, 2.463775157928467, 4.515203952789307, 2.0379579067230225, 1.9309076070785522, 3.2516918182373047, 3.298379421234131, 3.2985939979553223, 1.8113816976547241, 2.6868414878845215, 2.9787585735321045, 2.3978919982910156, 2.226193428039551, 3.7221133708953857, 5.490773677825928, 3.205479145050049, 2.143028497695923, 2.6349096298217773, 2.6803505420684814, 3.694861650466919, 2.7312140464782715, 2.751249313354492, 2.0967421531677246, 2.655501127243042, 3.6895503997802734, 3.503535270690918, 2.701129674911499, 2.8499133586883545, 2.966295003890991, 2.6120669841766357, 2.607651948928833, 3.5279433727264404, 3.4471943378448486, 2.3207597732543945, 2.860988140106201, 3.025282621383667, 3.407382011413574, 4.765913486480713, 3.0722899436950684, 1.9558923244476318, 2.539365291595459, 2.4722776412963867, 2.060525417327881, 3.4977657794952393, 3.0495998859405518, 3.4758503437042236, 2.491307258605957, 2.85829758644104, 3.5550968647003174, 3.1033248901367188, 4.455256462097168, 3.3302483558654785, 3.742307662963867, 2.2381174564361572, 2.134183406829834, 3.1484179496765137, 3.3149120807647705, 3.8118209838867188, 2.1116650104522705, 2.72856068611145, 3.514712333679199, 2.2869675159454346, 3.4466776847839355, 3.665628671646118, 2.9714081287384033, 3.646557569503784, 3.4827849864959717, 3.344609260559082, 2.108642578125, 3.2794888019561768, 1.9850046634674072, 2.524143695831299, 2.8418495655059814, 3.9494664669036865, 2.986294984817505, 2.7323412895202637, 2.9853503704071045, 3.748250961303711, 3.3288514614105225, 2.2635300159454346, 2.287287473678589, 3.080371618270874, 123.90509796142578, 113.228271484375, 142.7889404296875, 285.20208740234375, 143.43763732910156, 288.39703369140625, 147.12847900390625, 833.739501953125, 263.1085205078125, 230.8758544921875, 211.0775146484375, 130.36087036132812, 349.65374755859375, 148.56768798828125, 231.7088623046875, 129.79229736328125, 553.9769287109375, 74.697509765625, 120.74934387207031, 215.02981567382812, 153.46826171875, 501.5497131347656, 483.8274841308594, 228.09690856933594, 159.37225341796875, 325.1287536621094, 418.5770568847656, 193.37872314453125, 345.1876525878906, 231.42770385742188, 316.092529296875, 60.60575485229492, 50.23358154296875, 61.93157958984375, 353.7296142578125, 66.63970184326172, 111.66577911376953, 206.53929138183594, 199.15489196777344, 201.8323974609375, 96.5165023803711, 293.84832763671875, 299.9245300292969, 336.55792236328125, 450.1702880859375, 340.3243713378906, 280.0536193847656, 197.0678253173828, 317.7325744628906, 274.607177734375, 184.2386016845703, 342.7019958496094, 108.8035888671875, 249.2569122314453, 52.324588775634766, 359.5668640136719, 190.1190185546875, 617.511962890625, 399.1434631347656, 110.16336822509766, 231.21728515625, 231.66845703125, 151.97607421875, 272.4739990234375, 255.17205810546875, 195.54046630859375, 259.3341979980469, 66.49297332763672, 107.4246826171875, 81.7020492553711, 274.470703125, 211.3227081298828, 246.3841552734375, 217.29067993164062, 101.49053192138672, 191.14743041992188, 174.3076171875, 175.0185546875, 317.21630859375, 538.2781372070312, 94.38546752929688, 405.3900451660156, 150.188232421875, 47.27985382080078, 244.8145294189453, 241.5188751220703, 66.8436279296875, 54.63965606689453, 186.7639923095703, 102.67288970947266, 67.97616577148438, 350.7997131347656, 83.97066497802734, 169.23745727539062, 75.98877716064453, 356.5284729003906, 111.93029022216797, 135.19589233398438, 229.62158203125, 113.04618072509766, 436.3277893066406, 221.7940216064453, 141.20648193359375, 46.163818359375, 650.9581909179688, 476.7189025878906, 229.20022583007812, 172.08213806152344, 385.1859436035156, 86.70941162109375, 180.0453643798828, 130.02938842773438, 111.39579010009766, 421.5576477050781, 264.4720458984375, 186.01760864257812, 292.7580261230469, 269.4953308105469, 305.46832275390625, 151.42347717285156, 386.44927978515625, 90.1127700805664, 330.7048645019531, 60.976200103759766, 119.32364654541016, 283.2215576171875, 378.0790100097656, 111.99390411376953, 522.9334106445312, 221.7445068359375, 284.3655090332031, 125.20130920410156, 250.3416748046875, 113.7650146484375, 80.52214050292969, 98.6126480102539, 274.315673828125, 71.09599304199219, 462.1583557128906, 255.4541778564453, 62.005950927734375, 157.4987335205078, 388.2406311035156, 373.021240234375, 176.0669708251953, 154.94346618652344, 428.4379577636719, 140.81544494628906, 305.2802734375, 204.9212646484375, 66.80805206298828, 475.2658386230469, 244.3739013671875, 399.6383361816406, 140.42164611816406, 215.43569946289062, 253.58409118652344, 63.28143310546875, 98.39544677734375, 285.528076171875, 173.748779296875, 310.866943359375, 225.462646484375, 174.0477294921875, 132.3195343017578, 163.76084899902344, 76.3037109375, 75.51734924316406, 110.3243408203125, 130.0064239501953, 310.0499267578125, 55.45461654663086, 301.5085754394531, 257.1156005859375, 197.28173828125, 458.0341796875, 266.4433288574219, 128.21438598632812, 304.8023681640625, 313.6917419433594, 297.44195556640625, 276.78076171875, 517.4765625, 354.578125, 336.8313903808594, 310.81005859375, 431.1939697265625, 256.8548583984375, 271.99725341796875, 104.35576629638672, 416.3277893066406, 76.554931640625, 158.02467346191406, 110.33888244628906, 359.6656188964844, 276.2803955078125, 110.14409637451172, 351.3016662597656, 184.6283721923828, 116.8099365234375, 240.99729919433594, 195.58560180664062, 177.88780212402344, 91.70968627929688, 153.91384887695312, 171.84649658203125, 52.9510498046875, 218.53997802734375, 223.59130859375, 307.1856994628906, 198.0283203125, 115.89527130126953, 338.32135009765625, 368.4703674316406, 256.0755615234375, 813.8317260742188, 359.02874755859375, 119.97490692138672, 127.20000457763672, 426.1542053222656, 152.48394775390625, 194.2469482421875, 55.422119140625, 462.04632568359375, 50.144798278808594, 137.75320434570312, 202.4996795654297, 153.40362548828125, 306.2696533203125, 422.7691955566406, 469.7211608886719, 221.6257781982422, 373.70123291015625, 338.65771484375, 287.2113342285156, 414.546875, 258.23773193359375, 91.27404022216797, 156.14007568359375, 90.57203674316406, 211.1549530029297, 304.7933044433594, 84.51567840576172, 492.5943603515625, 333.7297058105469, 117.30596160888672, 85.7333984375, 100.40001678466797, 134.45664978027344, 60.38616943359375, 246.0877227783203, 160.34486389160156, 413.572021484375, 200.6073455810547, 383.829833984375, 191.1619415283203, 202.01953125, 218.40777587890625, 335.6528015136719, 246.9827880859375, 83.11390686035156, 399.697998046875, 354.9920959472656, 50.225341796875, 151.75062561035156, 99.95659637451172, 225.9193115234375, 68.0560302734375, 303.03802490234375, 419.2509765625, 90.75750732421875, 100.1083755493164, 106.24812316894531, 289.5604248046875, 404.1385803222656, 102.58563995361328, 190.54885864257812, 389.5063171386719, 259.37225341796875, 102.49687957763672, 348.08148193359375, 594.9720458984375, 124.56298828125, 441.4313049316406, 258.49072265625, 337.690185546875, 49.90684127807617, 78.66570281982422, 82.54734802246094, 181.4050750732422, 69.4935302734375, 109.53105926513672, 303.2277526855469, 80.9375228881836, 42.93315505981445, 139.8134307861328, 222.6326141357422, 291.0435791015625, 51.723934173583984, 50.33001708984375, 3.528409242630005, 3.0429906845092773, 2.5632617473602295, 2.7501208782196045, 3.137518882751465, 3.4901909828186035, 3.1474411487579346, 2.378366231918335, 2.7228505611419678, 1.9862972497940063, 2.1430046558380127, 2.788217067718506, 3.3342297077178955, 2.421891212463379, 2.315526008605957, 3.432149648666382, 2.1446027755737305, 3.9586880207061768, 2.9714813232421875, 1.5696783065795898, 2.7249486446380615, 2.7623541355133057, 3.5201895236968994, 1.2540010213851929, 2.296506404876709, 4.02241849899292, 1.9891341924667358, 1.572991967201233, 2.9295990467071533, 2.898791551589966, 2.017939567565918, 3.3761167526245117, 1.9491420984268188, 3.858332633972168, 2.9191982746124268, 3.6687726974487305, 3.497073173522949, 2.8148927688598633, 2.0541832447052, 2.846085786819458, 1.443432331085205, 3.509476900100708, 3.093621253967285, 2.7263214588165283, 1.5640869140625, 2.2620251178741455, 2.35809588432312, 3.75272274017334, 3.5014872550964355, 3.0450737476348877, 3.703312873840332, 2.38952898979187, 2.0992422103881836, 2.9345428943634033, 1.5526293516159058, 2.7502834796905518, 2.869767427444458, 2.771043062210083, 3.319960832595825, 2.312178611755371, 3.0926294326782227, 2.269052505493164, 1.7062853574752808, 3.902399778366089, 2.844918966293335, 3.04245662689209, 1.879892349243164, 2.09234356880188, 3.159625291824341, 2.5604522228240967, 2.0077717304229736, 2.358724594116211, 2.3718185424804688, 3.4232516288757324, 2.963818311691284, 1.7826082706451416, 1.5997533798217773, 1.8832964897155762, 3.5822994709014893, 2.9922289848327637, 2.9974608421325684, 2.4453537464141846, 2.870636224746704, 1.859236717224121, 1.661905288696289, 3.2866051197052, 2.3306779861450195, 2.1240015029907227, 4.009646415710449, 3.371434211730957, 3.255513906478882, 2.043037176132202, 1.6187543869018555, 1.6337919235229492, 3.693507194519043, 2.0084543228149414, 2.407083034515381, 3.9153544902801514, 2.358330011367798, 2.864271879196167, 2.641385555267334, 2.023503303527832, 3.151982307434082, 3.1482434272766113, 1.9721548557281494, 2.672259569168091, 2.2084245681762695, 2.15853214263916, 2.3925294876098633, 3.7519426345825195, 2.8386125564575195, 3.042414903640747, 1.4185171127319336, 3.6439831256866455, 3.1779229640960693, 3.638645887374878, 1.9954956769943237, 1.8843669891357422, 3.155266761779785, 1.9054818153381348, 2.6280908584594727, 2.251398801803589, 3.0453922748565674, 2.0709238052368164, 2.9930005073547363, 3.083857297897339, 1.95491361618042, 1.4840022325515747, 3.5111143589019775, 3.3861303329467773, 2.444423198699951, 4.077105522155762, 2.511002540588379, 3.0454187393188477, 3.198378324508667, 4.144626617431641, 2.2195651531219482, 1.9187231063842773, 3.5808398723602295, 1.615992546081543, 3.492324113845825, 1.8170274496078491, 2.084771156311035, 3.412785530090332, 2.3119211196899414, 3.254999876022339, 2.4818549156188965, 1.903420329093933, 3.194504976272583, 2.442223072052002, 2.88993763923645, 3.479020357131958, 2.4757161140441895, 2.676690101623535, 2.935795783996582, 2.1081857681274414, 3.0937132835388184, 4.028708457946777, 1.6614010334014893, 1.914420485496521, 1.9083614349365234, 1.4363030195236206, 1.9321831464767456, 2.395848274230957, 1.8397016525268555, 1.9761570692062378, 3.8087546825408936, 2.6996560096740723, 3.554521322250366, 2.947262763977051, 2.969439744949341, 3.700201988220215, 3.6540825366973877, 2.725170850753784, 1.3072212934494019, 3.915212392807007, 1.6769345998764038, 2.839139223098755, 2.3888158798217773, 2.512204170227051, 3.930983781814575, 3.2498714923858643, 2.37058162689209, 2.317246437072754, 2.1542043685913086, 2.7747645378112793, 2.128520965576172, 1.6462258100509644, 4.101639747619629, 3.569061279296875, 1.309132695198059, 2.112015724182129, 1.8707842826843262, 2.0818588733673096, 4.085597515106201, 3.512932300567627, 3.391524076461792, 3.6545188426971436, 2.137566566467285, 3.020379066467285, 3.5983476638793945, 2.068552255630493, 3.8371901512145996, 1.9185352325439453, 3.5768685340881348, 3.3151793479919434, 2.239051103591919, 1.6242446899414062, 2.301839828491211, 1.5863628387451172, 1.7243642807006836, 2.5188653469085693, 2.0626306533813477, 2.30582332611084, 2.5085606575012207, 3.458250045776367, 2.24381947517395, 2.275355339050293, 2.86836838722229, 2.793858528137207, 2.761025905609131, 2.052535057067871, 2.5961694717407227, 1.72003173828125, 3.0731327533721924, 2.6996748447418213, 2.1867761611938477, 3.8766162395477295, 2.787457227706909, 3.547703742980957, 2.713916540145874, 2.1694064140319824, 1.6339139938354492, 3.3797836303710938, 2.2910568714141846, 3.118340492248535, 2.1893720626831055, 3.3069441318511963, 3.311936616897583, 2.031614065170288, 1.9118223190307617, 2.7971391677856445, 2.7794885635375977, 3.2675487995147705, 3.3648464679718018, 2.7600255012512207, 2.5387942790985107, 2.347087860107422, 2.165684223175049, 2.449104070663452, 2.8747661113739014, 2.0351402759552, 3.8210670948028564, 2.4772403240203857, 3.1833698749542236, 2.8730974197387695, 2.3591110706329346, 3.1313412189483643, 3.0062224864959717, 2.283938407897949, 2.1455092430114746, 4.286126136779785, 1.8718252182006836, 2.9061005115509033, 2.836839437484741, 1.8525633811950684, 3.499903440475464, 1.7682092189788818, 2.732988119125366, 3.376415967941284, 2.7890710830688477, 2.4044878482818604, 2.621687650680542, 2.7074062824249268, 2.709409713745117, 1.6276787519454956, 3.0449540615081787, 2.115109443664551, 1.6690317392349243, 2.512134075164795, 2.072901725769043, 3.2169201374053955, 2.0775365829467773, 2.28476619720459, 1.9895023107528687, 2.579228401184082, 2.05379581451416, 3.6814029216766357, 3.166255474090576, 2.975520610809326, 2.1361169815063477, 3.307263135910034, 2.382643938064575, 3.5356950759887695, 1.7326955795288086, 2.399376630783081, 3.4028990268707275, 2.0202932357788086, 1.6273869276046753, 2.188939094543457, 0.2485504448413849, 0.25586846470832825, 0.25442466139793396, 0.23516014218330383, 0.24920719861984253, 0.3060019016265869, 0.30334657430648804, 0.3325217366218567, 0.2807479500770569, 0.2669239342212677, 0.2519278824329376, 0.2573736906051636, 0.2235104888677597, 0.24583357572555542, 0.26606911420822144, 0.30026450753211975, 0.3159477412700653, 0.31725919246673584, 0.2539133131504059, 0.23710717260837555, 0.27449434995651245, 0.22470919787883759, 0.23307175934314728, 0.22903163731098175, 0.1900823712348938, 0.2297978401184082, 0.2103031873703003, 0.2602509558200836, 0.17178133130073547, 0.2158837467432022, 0.2413257509469986, 0.26714155077934265, 0.20314334332942963, 0.23739027976989746, 0.24949924647808075, 0.23670466244220734, 0.21650242805480957, 0.23810191452503204, 0.308601975440979, 0.23386377096176147, 0.22912737727165222, 0.24888034164905548, 0.2773727774620056, 0.3178490102291107, 0.2010682076215744, 0.23776964843273163, 0.21404750645160675, 0.2627424895763397, 0.28070104122161865, 0.2711302638053894, 0.19133710861206055, 0.2338417023420334, 0.273342490196228, 0.23142535984516144, 0.23933978378772736, 0.20273756980895996, 0.20839717984199524, 0.2480067014694214, 0.19133113324642181, 0.265243798494339, 0.23076462745666504, 0.2070053070783615, 0.25779274106025696, 0.26093026995658875, 0.19690105319023132, 0.24289093911647797, 0.2959354817867279, 0.2482031136751175, 0.28039097785949707, 0.2704257667064667, 0.236961230635643, 0.2785869538784027, 0.2423272430896759, 0.1945614218711853, 0.2345595806837082, 0.3051876127719879, 0.1883867233991623, 0.22452180087566376, 0.2511274516582489, 0.2541804909706116, 0.20704425871372223, 0.23714232444763184, 0.22507964074611664, 0.2526592016220093, 0.26449453830718994, 0.24771685898303986, 0.2627738416194916, 0.2323039025068283, 0.2793530523777008, 0.2440105527639389, 0.20378468930721283, 0.2636152505874634, 0.3094923198223114, 0.26350298523902893, 0.2550106644630432, 0.23391178250312805, 0.24309805035591125, 0.2227126657962799, 0.2309487909078598, 0.20419195294380188, 0.23097428679466248, 0.1560661792755127, 0.3340202271938324, 0.27917906641960144, 0.3559393882751465, 0.23358485102653503, 0.3248118460178375, 0.24806725978851318, 0.27415731549263, 0.22068119049072266, 0.2732289731502533, 0.2382502555847168, 0.19960948824882507, 0.23804163932800293, 0.2250669300556183, 0.22593438625335693, 0.2283976674079895, 0.2587986886501312, 0.2792043685913086, 0.21060217916965485, 0.2168218493461609, 0.2407919317483902, 0.3173808157444, 0.2995162010192871, 0.28792688250541687, 0.1861969381570816, 0.22428424656391144, 0.2175326645374298, 0.27552172541618347, 0.2711358070373535, 0.29395365715026855, 0.2521575093269348, 0.2696433961391449, 0.20057450234889984, 0.20337951183319092, 0.2437092363834381, 0.2693336009979248, 0.2041509598493576, 0.2131466418504715, 0.23339758813381195, 0.29401928186416626, 0.23919759690761566, 0.21162156760692596, 0.21720661222934723, 0.27934718132019043, 0.23467005789279938, 0.16685669124126434, 0.2268311232328415, 0.25969865918159485, 0.2584357261657715, 0.30135488510131836, 0.3014690577983856, 0.22668159008026123, 0.3245474100112915, 0.29601889848709106, 0.2379193753004074, 0.23048633337020874, 0.29482120275497437, 0.184458389878273, 0.25933295488357544, 0.19718408584594727, 0.24114371836185455, 0.23424522578716278, 0.2364937663078308, 0.18886961042881012, 0.23774321377277374, 0.21434928476810455, 0.2456519603729248, 0.22200246155261993, 0.191108837723732, 0.26224485039711, 0.2926698327064514, 0.3177380859851837, 0.2593500018119812, 0.26741817593574524, 0.1946374922990799, 0.23849646747112274, 0.19181816279888153, 0.29048994183540344, 0.23125571012496948, 0.3193386197090149, 0.24533458054065704, 0.21835505962371826, 0.2947409749031067, 0.2464280128479004, 0.27333202958106995, 0.24403934180736542, 0.26415836811065674, 0.19302935898303986, 0.29336145520210266, 0.18766538798809052, 0.1877334862947464, 0.23002417385578156, 0.3097470998764038, 0.2394700050354004, 0.2740831673145294, 0.2017480581998825, 0.23772934079170227, 0.3234440088272095, 0.30721235275268555, 0.26232314109802246, 0.29395613074302673, 0.2961568236351013, 0.18991753458976746, 0.18608058989048004, 0.22574880719184875, 0.2934783101081848, 0.19352221488952637, 0.2611198425292969, 0.2724491059780121, 0.17015187442302704, 0.2620544135570526, 0.20424002408981323, 0.193831667304039, 0.20302923023700714, 0.1972522735595703, 0.27246707677841187, 0.23836742341518402, 0.24121688306331635, 0.25180163979530334, 0.28409337997436523, 0.15413667261600494, 0.2518860697746277, 0.23721003532409668, 0.30298763513565063, 0.263126403093338, 0.2837332487106323, 0.2494763880968094, 0.3095058500766754, 0.2644391655921936, 0.296916127204895, 0.17683862149715424, 0.16989253461360931, 0.24594375491142273, 0.20568667352199554, 0.24371352791786194, 0.2065858095884323, 0.3183974325656891, 0.21107123792171478, 0.2949376106262207, 0.24918487668037415, 0.27132704854011536, 0.22150716185569763, 0.24688954651355743, 0.2494874745607376, 0.27505481243133545, 0.24397265911102295, 0.328255295753479, 0.2757439911365509, 0.24279631674289703, 0.263742059469223, 0.24486316740512848, 0.22943133115768433, 0.27061498165130615, 0.23489713668823242, 0.23329901695251465, 0.24242663383483887, 0.2826906442642212, 0.2848320007324219, 0.2168521136045456, 0.3056298494338989, 0.2950339913368225, 0.21718920767307281, 0.22032351791858673, 0.2674383819103241, 0.2760278284549713, 0.27666404843330383, 0.2524013817310333, 0.2525295913219452, 0.25191542506217957, 0.22746863961219788, 0.22369681298732758, 0.20425094664096832, 0.1933840960264206, 0.2644205689430237, 0.28284960985183716, 0.28799787163734436, 0.24835515022277832, 0.2529318928718567, 0.23401395976543427, 0.23414185643196106, 0.2686617970466614, 0.20224682986736298, 0.18146657943725586, 0.1583973467350006, 0.20160773396492004, 0.283448725938797, 0.22050727903842926, 0.22443556785583496, 0.2748202085494995, 0.21974042057991028, 0.21993286907672882, 0.20031318068504333, 0.18349528312683105, 0.2104303538799286, 0.23747222125530243, 0.26884889602661133, 0.25029653310775757, 0.27025043964385986, 0.20697443187236786, 2.4306259155273438, 3.4812679290771484, 1.8274946212768555, 3.109314441680908, 3.7244515419006348, 3.2997961044311523, 2.5821373462677, 2.7337117195129395, 1.9385032653808594, 2.9682488441467285, 4.277029514312744, 3.3588688373565674, 2.058903217315674, 1.9323351383209229, 2.100416898727417, 3.170612096786499, 2.347226142883301, 2.140064001083374, 4.714186191558838, 2.2137982845306396, 3.163662910461426, 2.8893158435821533, 2.842741012573242, 4.063937664031982, 3.0554745197296143, 2.578084945678711, 3.4283809661865234, 2.6469521522521973, 3.8455357551574707, 1.7995394468307495, 3.5672600269317627, 3.463531494140625, 2.509721040725708, 3.4576549530029297, 3.3740150928497314, 2.2981715202331543, 4.520545959472656, 2.005075216293335, 3.506420850753784, 2.9855427742004395, 2.920001268386841, 3.2220420837402344, 3.8187077045440674, 2.832536458969116, 1.759855031967163, 2.302513599395752, 3.7015035152435303, 2.616656541824341, 3.645472288131714, 3.300612688064575, 2.69858455657959, 2.734300374984741, 3.636812686920166, 3.2770237922668457, 2.809786558151245, 2.266596794128418, 3.2083985805511475, 2.546623706817627, 3.106266498565674, 3.516150712966919, 2.3651328086853027, 2.3085615634918213, 3.3918237686157227, 2.7847230434417725, 2.024136543273926, 2.9629833698272705, 3.65746808052063, 3.4536502361297607, 4.688391208648682, 2.6747632026672363, 2.3407106399536133, 4.494596481323242, 2.4891207218170166, 1.860848307609558, 3.0667452812194824, 1.7472727298736572, 2.990190267562866, 2.5087056159973145, 4.262966156005859, 3.7531559467315674, 1.7604055404663086, 2.475029230117798, 4.711662292480469, 2.4160983562469482, 1.9702503681182861, 2.477308511734009, 2.2529759407043457, 1.720312476158142, 3.0711162090301514, 2.9592907428741455, 2.6877048015594482, 2.880176305770874, 2.8759045600891113, 1.9410158395767212, 5.155066967010498, 2.848271131515503, 2.4163904190063477, 4.191325664520264, 3.3880162239074707, 4.839191913604736, 3.3735034465789795, 1.8481844663619995, 4.4356536865234375, 2.659424304962158, 3.7818639278411865, 3.619371175765991, 3.82004451751709, 2.6873435974121094, 2.6463654041290283, 3.521751880645752, 2.2917022705078125, 3.790513753890991, 3.547379732131958, 3.305392265319824, 3.0163028240203857, 4.293869495391846, 2.708665132522583, 2.439425230026245, 3.8158938884735107, 3.7296464443206787, 4.035722732543945, 3.6987035274505615, 4.497554779052734, 3.1631996631622314, 3.4165401458740234, 2.5781543254852295, 2.4177565574645996, 4.359632968902588, 2.6353917121887207, 2.3009021282196045, 3.349168539047241, 3.0409176349639893, 3.126439332962036, 4.632780075073242, 3.7404613494873047, 3.3344151973724365, 2.128584146499634, 2.8471896648406982, 2.9774582386016846, 4.044825553894043, 2.945436954498291, 2.6804585456848145, 2.5991039276123047, 2.257549285888672, 3.360440969467163, 4.1462836265563965, 2.9139926433563232, 2.1230313777923584, 2.2125320434570312, 4.148934841156006, 3.3297131061553955, 2.9901764392852783, 5.6390275955200195, 3.4960038661956787, 3.5418083667755127, 2.159818172454834, 2.965045690536499, 2.717421770095825, 3.528259754180908, 3.4971728324890137, 1.796364426612854, 2.3695340156555176, 3.749859571456909, 3.718402624130249, 2.559377670288086, 3.8163392543792725, 2.4602065086364746, 3.587158679962158, 2.33471941947937, 2.331136703491211, 3.573474645614624, 2.2499496936798096, 3.4968719482421875, 2.2597644329071045, 3.707319974899292, 2.5632176399230957, 3.0047671794891357, 2.5957088470458984, 2.4749743938446045, 3.20609974861145, 4.554459095001221, 2.2083330154418945, 2.665393114089966, 3.1637017726898193, 2.300126552581787, 3.848146915435791, 4.233337879180908, 1.9734777212142944, 1.859702706336975, 1.9860302209854126, 4.2387237548828125, 2.825972318649292, 3.595555543899536, 3.148853063583374, 1.9292176961898804, 3.3600120544433594, 4.245110511779785, 5.436522006988525, 3.072993040084839, 2.3134121894836426, 2.91117787361145, 2.7774388790130615, 4.31654167175293, 4.211012363433838, 3.6041958332061768, 2.4030258655548096, 3.089627504348755, 3.0860490798950195, 3.1355321407318115, 2.8166069984436035, 3.3612847328186035, 3.1031084060668945, 3.5421395301818848, 2.608469247817993, 3.7435107231140137, 3.4832048416137695, 2.573101043701172, 2.265258550643921, 2.6845734119415283, 3.4324581623077393, 1.9321250915527344, 2.824927568435669, 2.986096143722534, 2.5816545486450195, 2.485274076461792, 3.1896159648895264, 3.7259151935577393, 2.6793651580810547, 2.159693717956543, 3.0514190196990967, 4.789897918701172, 1.985464096069336, 2.2400341033935547, 2.342406988143921, 2.8788976669311523, 2.239001512527466, 3.6228137016296387, 3.9220714569091797, 3.3907902240753174, 2.7343204021453857, 3.5475597381591797, 2.8434581756591797, 3.277794361114502, 3.786774158477783, 2.470766305923462, 3.2654716968536377, 3.4882993698120117, 2.7031822204589844, 3.333148717880249, 2.426431179046631, 1.9698656797409058, 3.056694984436035, 1.9998763799667358, 3.4448235034942627, 3.4871411323547363, 3.1748135089874268, 3.613176107406616, 4.795228958129883, 2.065216302871704, 3.651578187942505, 3.3028271198272705, 2.540412425994873, 3.1663835048675537, 2.9010441303253174, 2.196261405944824, 3.743803024291992, 2.2816383838653564, 3.3112003803253174, 1.9714035987854004, 2.8515026569366455, 2.775249481201172, 3.1457760334014893, 4.303833961486816, 3.2186038494110107, 4.148491382598877, 4.127676010131836, 4.951848030090332, 2.8078296184539795, 2.5932083129882812, 2.2383370399475098, 3.2845189571380615, 3.4510819911956787, 3.594465970993042, 2.793860673904419, 3.5825536251068115, 1.8979002237319946, 3.33011531829834, 3.6931087970733643, 2.7104363441467285, 3.977116107940674, 4.91497278213501, 2.4482498168945312, 2.8172807693481445, 2.0779471397399902, 3.5033509731292725, 1.9486230611801147, 2.240349292755127, 2.02396559715271, 2.713688850402832, 3.4350907802581787, 102.19464874267578, 157.61053466796875, 177.10975646972656, 225.77015686035156, 57.64569091796875, 182.0247802734375, 142.21780395507812, 305.5382080078125, 78.859619140625, 368.8814697265625, 419.4523620605469, 256.9443359375, 516.1632080078125, 113.86306762695312, 177.79026794433594, 143.29747009277344, 109.36872863769531, 176.4298858642578, 98.2289047241211, 125.362060546875, 412.47216796875, 340.0162353515625, 194.20860290527344, 77.20303344726562, 137.32997131347656, 158.5830078125, 302.3235778808594, 253.03872680664062, 401.6669006347656, 245.7464599609375, 215.197021484375, 225.34735107421875, 275.1268310546875, 275.0653991699219, 142.7304229736328, 278.149169921875, 315.5241394042969, 58.77207946777344, 128.6112518310547, 163.40805053710938, 161.15496826171875, 98.96149444580078, 181.96124267578125, 217.19287109375, 48.255615234375, 65.85088348388672, 163.4515380859375, 164.1759490966797, 131.81658935546875, 289.96331787109375, 515.2523193359375, 75.583251953125, 164.18186950683594, 56.979305267333984, 266.51904296875, 332.6527404785156, 230.9936065673828, 282.83935546875, 78.75439453125, 326.5966796875, 253.85369873046875, 211.3728485107422, 320.521484375, 303.912841796875, 143.70245361328125, 497.34307861328125, 184.95556640625, 162.04168701171875, 172.55029296875, 186.25540161132812, 186.7462921142578, 204.5786895751953, 92.19326782226562, 201.19992065429688, 239.3609161376953, 208.7517547607422, 249.65911865234375, 99.87931060791016, 298.9500732421875, 259.12884521484375, 381.14068603515625, 265.96112060546875, 218.3163604736328, 79.709228515625, 437.7557678222656, 169.4639434814453, 151.24609375, 285.893310546875, 505.4691162109375, 480.00054931640625, 240.52337646484375, 613.0146484375, 148.19496154785156, 336.3104553222656, 267.6689453125, 54.2010498046875, 286.7224426269531, 251.0917510986328, 241.7206268310547, 240.30967712402344, 273.47125244140625, 275.9188232421875, 497.7013854980469, 119.61417388916016, 486.136474609375, 53.06610107421875, 201.44593811035156, 160.00514221191406, 353.826171875, 136.8951416015625, 364.248779296875, 76.48129272460938, 313.95709228515625, 639.1834106445312, 231.88311767578125, 452.3383483886719, 537.957763671875, 57.99407196044922, 74.686279296875, 107.68826293945312, 238.373046875, 104.4398193359375, 264.84307861328125, 182.6712646484375, 301.7926025390625, 156.50526428222656, 53.55462646484375, 125.58939361572266, 198.571044921875, 351.731201171875, 307.8209228515625, 113.82962036132812, 132.678466796875, 208.14170837402344, 249.5433807373047, 368.72589111328125, 133.361572265625, 788.00732421875, 215.0701141357422, 177.9694366455078, 158.01348876953125, 267.45281982421875, 565.9867553710938, 261.4216613769531, 91.6673812866211, 317.5763854980469, 74.69658660888672, 224.0203094482422, 364.69195556640625, 373.8148498535156, 135.15765380859375, 115.71536254882812, 171.9691162109375, 387.8110046386719, 374.2359313964844, 312.79327392578125, 191.1192169189453, 365.3656311035156, 265.59454345703125, 225.79803466796875, 621.52685546875, 83.00244140625, 62.02117919921875, 314.2782287597656, 170.54530334472656, 215.0830078125, 318.1632995605469, 318.9162292480469, 112.5062255859375, 70.4268798828125, 160.32894897460938, 200.6639404296875, 347.2938537597656, 384.733154296875, 154.7001953125, 492.7063293457031, 190.77061462402344, 406.1298828125, 191.41514587402344, 133.4066925048828, 171.9140167236328, 231.23977661132812, 112.2734375, 336.10406494140625, 195.14794921875, 39.29235076904297, 273.3595886230469, 141.26760864257812, 147.12025451660156, 202.3616485595703, 377.6769104003906, 64.9124755859375, 58.640380859375, 160.6517791748047, 49.449462890625, 174.06797790527344, 184.2468719482422, 217.2830810546875, 259.72900390625, 105.3143310546875, 81.22443389892578, 47.29204177856445, 97.09162902832031, 134.90072631835938, 268.0121765136719, 421.878662109375, 237.74386596679688, 199.9169464111328, 237.5379638671875, 224.7076873779297, 61.89276123046875, 69.6082534790039, 182.40576171875, 274.5781555175781, 124.2991943359375, 237.5991973876953, 377.086669921875, 214.0030059814453, 129.17567443847656, 97.8993911743164, 139.41534423828125, 49.21255111694336, 314.9158935546875, 121.9326171875, 130.05091857910156, 179.0574188232422, 144.45973205566406, 307.4475402832031, 81.4444580078125, 392.7704162597656, 134.782958984375, 273.2789306640625, 145.615478515625, 382.1878967285156, 56.90423583984375, 156.1471710205078, 269.93853759765625, 438.9332580566406, 111.074951171875, 418.4471130371094, 49.2567138671875, 177.1346893310547, 183.87159729003906, 261.6712646484375, 70.75617980957031, 267.0488586425781, 147.339599609375, 507.27874755859375, 74.2169189453125, 433.0829162597656, 542.9437866210938, 910.5999145507812, 356.38922119140625, 136.59678649902344, 109.9945068359375, 78.42694091796875, 517.5238037109375, 488.18804931640625, 151.570068359375, 255.10400390625, 339.6805419921875, 431.6346130371094, 235.77685546875, 431.0516357421875, 298.8167724609375, 241.187255859375, 208.84622192382812, 333.5295104980469, 470.2750549316406, 230.39268493652344, 225.16058349609375, 75.39588928222656, 221.119140625, 50.77913284301758, 230.20330810546875, 88.85773468017578, 409.8792724609375, 343.7674865722656, 120.3026123046875, 129.3978271484375, 450.1330261230469, 139.325927734375, 249.567138671875, 183.1322021484375, 54.01613998413086, 60.3538932800293, 170.0182342529297, 659.3930053710938, 174.98963928222656, 77.523193359375, 252.23287963867188, 193.7093963623047, 211.52061462402344, 108.24432373046875, 323.9289245605469, 199.45274353027344, 235.43280029296875, 376.2570495605469, 70.38590240478516, 262.6872863769531, 1.852734923362732, 2.602231025695801, 2.865161180496216, 1.7105162143707275, 3.165590763092041, 3.6012933254241943, 2.47463059425354, 2.5577878952026367, 2.3231711387634277, 2.0677804946899414, 1.9216244220733643, 3.460574150085449, 2.0641565322875977, 2.003096580505371, 2.7878823280334473, 2.485171318054199, 3.019911527633667, 2.153193712234497, 3.003148078918457, 2.4219110012054443, 3.049332857131958, 2.561893939971924, 2.8546838760375977, 3.402787446975708, 1.330933690071106, 1.6438323259353638, 3.168950319290161, 1.622462272644043, 3.4466392993927, 2.092160224914551, 2.621055841445923, 3.549015998840332, 1.6684789657592773, 2.6768102645874023, 4.160940647125244, 2.5502219200134277, 3.7811248302459717, 2.7529399394989014, 3.3818647861480713, 3.404486894607544, 2.3079347610473633, 2.3715553283691406, 3.151728391647339, 1.8310292959213257, 2.4120140075683594, 1.8831208944320679, 2.866534471511841, 2.44085955619812, 2.6119091510772705, 1.9999175071716309, 3.2513177394866943, 2.512697458267212, 2.1727514266967773, 2.07190203666687, 2.8784286975860596, 3.1054413318634033, 2.1491453647613525, 2.9157609939575195, 3.584630012512207, 2.5991485118865967, 1.827565312385559, 3.878603935241699, 1.7366869449615479, 2.416965961456299, 2.7212862968444824, 1.5380141735076904, 3.388306140899658, 1.9141976833343506, 2.373654365539551, 2.0341219902038574, 3.1279003620147705, 3.2920422554016113, 2.4590845108032227, 1.759791374206543, 2.0355162620544434, 1.741138219833374, 3.4752514362335205, 3.649043560028076, 2.991184711456299, 2.623692512512207, 2.9322521686553955, 1.953455924987793, 2.3761303424835205, 1.9044541120529175, 4.073206901550293, 4.061919212341309, 3.0948503017425537, 2.9113683700561523, 2.2344179153442383, 3.4115679264068604, 3.432654619216919, 2.0358171463012695, 2.6033036708831787, 1.9618215560913086, 2.29594087600708, 2.8887364864349365, 2.183840751647949, 2.3070781230926514, 1.923169493675232, 2.7527878284454346, 3.487910747528076, 3.9033689498901367, 3.677201509475708, 2.852475166320801, 2.563551664352417, 3.590446949005127, 2.66618275642395, 2.377598762512207, 3.3170406818389893, 3.5064971446990967, 2.7383522987365723, 2.8717947006225586, 2.7525076866149902, 2.644688606262207, 3.378249168395996, 2.7593657970428467, 3.590879201889038, 2.8500397205352783, 2.1306447982788086, 2.910379648208618, 2.7567873001098633, 2.013068199157715, 2.058222532272339, 2.247076988220215, 2.1431901454925537, 3.137639045715332, 2.4267265796661377, 2.098114013671875, 3.292360544204712, 3.077162504196167, 1.759987473487854, 2.6599700450897217, 3.0063393115997314, 2.1224091053009033, 2.5664329528808594, 1.6018476486206055, 1.5901180505752563, 3.4876255989074707, 3.0375397205352783, 3.379103899002075, 2.4315171241760254, 1.5177481174468994, 2.092251777648926, 2.368610382080078, 1.5460309982299805, 3.767704963684082, 2.726559638977051, 1.3418763875961304, 2.5585646629333496, 1.9329653978347778, 2.236128807067871, 3.401615858078003, 3.1676063537597656, 3.665639638900757, 2.8037025928497314, 2.0689516067504883, 3.4301860332489014, 2.1300997734069824, 2.75472092628479, 2.5426383018493652, 2.9713475704193115, 1.6577200889587402, 3.2082836627960205, 2.0298399925231934, 1.8981930017471313, 2.2286179065704346, 2.4724884033203125, 2.064995765686035, 3.593055009841919, 2.038773775100708, 2.8794777393341064, 3.8566601276397705, 1.688865065574646, 2.8669512271881104, 2.0957095623016357, 2.653090238571167, 2.552004814147949, 2.3144240379333496, 3.3697690963745117, 2.8845934867858887, 2.252434730529785, 2.4955575466156006, 3.412705659866333, 1.836440086364746, 2.3093347549438477, 2.852146863937378, 2.194516181945801, 2.1649396419525146, 2.2917068004608154, 3.979748487472534, 2.7916042804718018, 2.393548011779785, 3.252692461013794, 2.315803289413452, 3.580582857131958, 2.0871171951293945, 1.393141746520996, 2.723832368850708, 2.1630029678344727, 2.987614631652832, 3.1901512145996094, 2.0004384517669678, 1.903468132019043, 2.154902458190918, 2.246333360671997, 3.027749538421631, 2.9769344329833984, 2.0976781845092773, 2.4625582695007324, 3.610346794128418, 3.132561683654785, 3.118708372116089, 1.4392250776290894, 2.4909884929656982, 3.235790252685547, 2.239794969558716, 2.874221086502075, 3.5316579341888428, 3.1170146465301514, 3.478407144546509, 2.9886887073516846, 2.8290672302246094, 2.7880983352661133, 1.876338005065918, 3.2156999111175537, 2.3409831523895264, 3.6959755420684814, 2.919186592102051, 2.0890893936157227, 3.2397892475128174, 3.5307424068450928, 2.993375539779663, 1.5351977348327637, 2.2702584266662598, 2.2544374465942383, 2.317835569381714, 3.486912727355957, 2.2901997566223145, 2.528505325317383, 3.692671060562134, 4.001791954040527, 2.5371484756469727, 3.7445931434631348, 3.2398808002471924, 2.1457223892211914, 2.8773186206817627, 3.984286308288574, 2.134343147277832, 1.6159396171569824, 2.8655717372894287, 2.6024398803710938, 2.749455451965332, 2.607402801513672, 2.4681973457336426, 2.181539297103882, 1.4662084579467773, 2.433743476867676, 2.4190402030944824, 2.639697551727295, 2.9958527088165283, 2.942572593688965, 2.9862115383148193, 3.8376595973968506, 1.8757314682006836, 2.970170259475708, 3.415411949157715, 3.0579490661621094, 2.67446231842041, 1.9759457111358643, 2.048570394515991, 3.2380101680755615, 2.942033529281616, 2.58400821685791, 1.680001974105835, 2.8099987506866455, 1.3451757431030273, 3.135136604309082, 3.56447696685791, 2.5066709518432617, 2.0047805309295654, 1.8656624555587769, 3.1944997310638428, 3.017108201980591, 3.0817201137542725, 1.8117738962173462, 2.991741895675659, 3.75671124458313, 2.595189094543457, 3.0935909748077393, 3.335892915725708, 2.752570152282715, 1.4733800888061523, 2.8629417419433594, 2.45052433013916, 2.412735939025879, 3.055864095687866, 2.293259620666504, 2.9648377895355225, 3.0035204887390137, 2.6130897998809814, 0.25157642364501953, 0.22271205484867096, 0.2815854549407959, 0.21929603815078735, 0.22251932322978973, 0.2792297601699829, 0.3583560883998871, 0.23969604074954987, 0.2902742326259613, 0.1907518357038498, 0.3963886499404907, 0.2784424126148224, 0.27644115686416626, 0.19168587028980255, 0.26267409324645996, 0.2378423660993576, 0.2576979100704193, 0.24875347316265106, 0.2858964204788208, 0.2421497106552124, 0.27269938588142395, 0.2903561294078827, 0.27568742632865906, 0.18607142567634583, 0.24656051397323608, 0.29677051305770874, 0.2511445879936218, 0.22802884876728058, 0.2711956202983856, 0.3010718524456024, 0.26238712668418884, 0.275973379611969, 0.23082488775253296, 0.17256540060043335, 0.22040878236293793, 0.2938261330127716, 0.22106432914733887, 0.23478373885154724, 0.20450764894485474, 0.24827606976032257, 0.24613982439041138, 0.2501547038555145, 0.29009100794792175, 0.16420939564704895, 0.21417716145515442, 0.23474226891994476, 0.30438485741615295, 0.2099762260913849, 0.2285061925649643, 0.23874258995056152, 0.25999715924263, 0.2933511734008789, 0.2820950746536255, 0.3223196268081665, 0.2883603572845459, 0.20452602207660675, 0.2737586796283722, 0.21466541290283203, 0.20563936233520508, 0.23867300152778625, 0.2670043110847473, 0.2741611897945404, 0.25703075528144836, 0.28810325264930725, 0.20989499986171722, 0.29557520151138306, 0.2693728506565094, 0.32402366399765015, 0.32146644592285156, 0.28321129083633423, 0.2819816768169403, 0.22024114429950714, 0.2763688266277313, 0.24903258681297302, 0.2631833553314209, 0.2451169490814209, 0.25284361839294434, 0.2540631890296936, 0.2918337285518646, 0.25132572650909424, 0.261089026927948, 0.27553823590278625, 0.22609305381774902, 0.24171145260334015, 0.22312068939208984, 0.3066512942314148, 0.23534667491912842, 0.21735042333602905, 0.2895541191101074, 0.21805961430072784, 0.2562601864337921, 0.30268821120262146, 0.2283341884613037, 0.2590589225292206, 0.2963390350341797, 0.30350440740585327, 0.218907430768013, 0.193337544798851, 0.25224369764328003, 0.29888126254081726, 0.32416388392448425, 0.2453937828540802, 0.2570771872997284, 0.21520283818244934, 0.25003185868263245, 0.2549102306365967, 0.20055213570594788, 0.2576071619987488, 0.2762829661369324, 0.23190751671791077, 0.19968700408935547, 0.24674664437770844, 0.2746168375015259, 0.1967637538909912, 0.2708296775817871, 0.23281340301036835, 0.2736794650554657, 0.2798582911491394, 0.20987766981124878, 0.21838828921318054, 0.29358726739883423, 0.26353976130485535, 0.19936330616474152, 0.2825183570384979, 0.2345481812953949, 0.2754528820514679, 0.3048199713230133, 0.21937033534049988, 0.1712357997894287, 0.2744702100753784, 0.24182498455047607, 0.26929476857185364, 0.28012943267822266, 0.23370163142681122, 0.17481525242328644, 0.2413763701915741, 0.2664410173892975, 0.35372352600097656, 0.2819962203502655, 0.22436797618865967, 0.26085713505744934, 0.21107490360736847, 0.24236591160297394, 0.23599693179130554, 0.17715001106262207, 0.1899176388978958, 0.25864192843437195, 0.21234361827373505, 0.26450783014297485, 0.21517470479011536, 0.30620792508125305, 0.23279955983161926, 0.29478228092193604, 0.21441100537776947, 0.27758219838142395, 0.23868343234062195, 0.2637162208557129, 0.23854082822799683, 0.2233482003211975, 0.21977019309997559, 0.2197573482990265, 0.2882186472415924, 0.27384865283966064, 0.28332966566085815, 0.29765623807907104, 0.2845613658428192, 0.16730765998363495, 0.2652009427547455, 0.29043105244636536, 0.24087446928024292, 0.295660138130188, 0.27459415793418884, 0.21149268746376038, 0.2312958538532257, 0.1765735149383545, 0.2553875148296356, 0.18775533139705658, 0.2571837902069092, 0.1985447257757187, 0.33979177474975586, 0.24045130610466003, 0.24718892574310303, 0.23225215077400208, 0.2688746750354767, 0.2829928696155548, 0.2236723154783249, 0.2804693281650543, 0.23953786492347717, 0.2163112908601761, 0.2551316022872925, 0.2716480493545532, 0.26567843556404114, 0.24392631649971008, 0.20726779103279114, 0.30871346592903137, 0.24464744329452515, 0.1989109069108963, 0.23467741906642914, 0.303291380405426, 0.24155539274215698, 0.2902641296386719, 0.23016388714313507, 0.24099673330783844, 0.2358582317829132, 0.29420438408851624, 0.2594934105873108, 0.1907000094652176, 0.22283431887626648, 0.22855244576931, 0.25771206617355347, 0.258179247379303, 0.2818794846534729, 0.296908438205719, 0.20947451889514923, 0.24954737722873688, 0.1712481826543808, 0.23093749582767487, 0.2270171344280243, 0.223515123128891, 0.31393101811408997, 0.22548246383666992, 0.25403156876564026, 0.2219610959291458, 0.254178911447525, 0.3003791272640228, 0.29540395736694336, 0.3561760485172272, 0.32232236862182617, 0.23716826736927032, 0.2389305830001831, 0.2173066884279251, 0.19558200240135193, 0.2558671534061432, 0.2774558663368225, 0.2615734934806824, 0.22457075119018555, 0.299102246761322, 0.2784731686115265, 0.21478377282619476, 0.22812604904174805, 0.24369433522224426, 0.24745464324951172, 0.24542276561260223, 0.2978765070438385, 0.23976744711399078, 0.16043396294116974, 0.19583521783351898, 0.27068549394607544, 0.2663837671279907, 0.2043541669845581, 0.20845851302146912, 0.24217276275157928, 0.25313541293144226, 0.20708182454109192, 0.2284971922636032, 0.24731124937534332, 0.23376010358333588, 0.20700465142726898, 0.33015280961990356, 0.264430969953537, 0.2974097430706024, 0.23092569410800934, 0.23364299535751343, 0.24855631589889526, 0.25663283467292786, 0.21903793513774872, 0.1893564909696579, 0.261668860912323, 0.3173291087150574, 0.19834987819194794, 0.2810160517692566, 0.22810427844524384, 0.23571623861789703, 0.24077476561069489, 0.22130607068538666, 0.2910717725753784, 0.29607847332954407, 0.23340508341789246, 0.27916228771209717, 0.23180346190929413, 0.23207023739814758, 0.2572912275791168, 0.27108755707740784, 0.26581433415412903, 0.20232105255126953, 0.28450366854667664, 0.2835060954093933, 0.2514191269874573, 0.2887129783630371, 0.26333948969841003, 0.24123454093933105, 0.23698768019676208, 0.2709289491176605, 0.2635626196861267, 0.22229324281215668, 0.2673397660255432, 0.2923435568809509, 0.3118009567260742, 0.2612132728099823, 0.20690424740314484, 2.2638461589813232, 1.6323130130767822, 1.895035982131958, 4.157836437225342, 3.3973934650421143, 4.301329135894775, 2.4020285606384277, 3.4485888481140137, 2.914459466934204, 2.892620086669922, 2.8790318965911865, 2.1904072761535645, 4.360734939575195, 2.397974729537964, 4.298666477203369, 2.8228633403778076, 3.2485222816467285, 3.9727425575256348, 3.8235714435577393, 2.5000338554382324, 2.2925920486450195, 2.17157244682312, 3.1827518939971924, 3.1055169105529785, 2.1958677768707275, 3.5015645027160645, 3.2658069133758545, 2.413320302963257, 3.657351016998291, 2.5255589485168457, 2.004828691482544, 2.839186429977417, 3.1842596530914307, 3.0556600093841553, 3.3465118408203125, 2.26054048538208, 3.34124493598938, 2.223202705383301, 4.030695915222168, 3.386630058288574, 2.1042351722717285, 3.00140380859375, 2.9410643577575684, 3.4283981323242188, 1.9024766683578491, 2.3805954456329346, 2.769463062286377, 4.151924133300781, 4.099104404449463, 3.198606491088867, 4.234945774078369, 3.1823577880859375, 2.919527530670166, 3.037421464920044, 3.398724317550659, 3.1816203594207764, 1.7808135747909546, 4.021547317504883, 2.4258720874786377, 2.1033356189727783, 2.612520694732666, 4.927944183349609, 3.177380323410034, 2.1583545207977295, 2.8019425868988037, 2.3020474910736084, 4.563801288604736, 5.141214370727539, 4.958492279052734, 3.7202720642089844, 2.9382219314575195, 2.3169705867767334, 2.371345043182373, 2.2449023723602295, 3.1888225078582764, 2.856917142868042, 3.0012199878692627, 2.7272515296936035, 1.962252140045166, 4.0115556716918945, 4.926014423370361, 3.6105382442474365, 2.9416873455047607, 1.914737343788147, 3.299285411834717, 1.9395830631256104, 2.495788097381592, 2.771456241607666, 4.724443435668945, 4.300014019012451, 3.1966075897216797, 2.5466530323028564, 3.461787700653076, 2.335141897201538, 2.423847198486328, 2.4489309787750244, 2.750108480453491, 4.20180606842041, 3.6235759258270264, 2.7108311653137207, 2.4560625553131104, 3.4031155109405518, 2.1100857257843018, 2.042371988296509, 2.5385327339172363, 3.0123050212860107, 5.4188032150268555, 2.707777738571167, 3.431272506713867, 3.408015012741089, 2.791199207305908, 2.7284133434295654, 2.9009861946105957, 2.6965548992156982, 3.0574169158935547, 3.3538694381713867, 2.6190884113311768, 2.9832820892333984, 3.1738152503967285, 3.2734215259552, 2.9341065883636475, 3.66475248336792, 3.804133415222168, 3.212601900100708, 3.0711135864257812, 3.363201141357422, 3.191624164581299, 3.138843297958374, 2.890704393386841, 3.3962833881378174, 2.1263322830200195, 3.074866533279419, 4.106557846069336, 3.1842002868652344, 2.7824089527130127, 2.456409454345703, 2.026062488555908, 2.7841389179229736, 3.772775411605835, 2.3787426948547363, 4.395439624786377, 3.9755494594573975, 2.0655364990234375, 2.8695952892303467, 2.8159103393554688, 2.686509370803833, 1.7425577640533447, 2.9361236095428467, 4.376062393188477, 3.7898595333099365, 4.7027106285095215, 3.3650732040405273, 2.7947323322296143, 2.9314796924591064, 3.7885923385620117, 2.00716233253479, 2.8758482933044434, 3.512150287628174, 2.2088818550109863, 3.5400164127349854, 2.7454452514648438, 3.250857353210449, 5.696906566619873, 1.8538286685943604, 3.5203874111175537, 2.867140531539917, 3.5200469493865967, 5.313762664794922, 2.207897186279297, 3.398515462875366, 1.9777426719665527, 2.8095955848693848, 2.276482582092285, 3.022374153137207, 2.179669141769409, 3.7021894454956055, 2.9274051189422607, 2.647761583328247, 2.6347689628601074, 4.031942367553711, 2.3433403968811035, 2.4109060764312744, 4.032166481018066, 3.032318592071533, 3.0544610023498535, 3.6508171558380127, 4.275393486022949, 3.7050774097442627, 1.9476741552352905, 2.2415478229522705, 3.019953489303589, 3.223022937774658, 2.861544132232666, 3.535442352294922, 4.987905979156494, 2.993281841278076, 3.5117974281311035, 3.783686637878418, 3.2653448581695557, 2.6234054565429688, 2.4361233711242676, 2.2469799518585205, 2.479830265045166, 3.0849697589874268, 4.057861328125, 2.7804360389709473, 2.621244430541992, 3.505007266998291, 2.624774217605591, 4.8042731285095215, 3.2794926166534424, 2.688436508178711, 4.086385726928711, 3.462125778198242, 2.6250839233398438, 2.954570770263672, 3.5073399543762207, 2.8306567668914795, 2.9012467861175537, 2.610276937484741, 3.6788060665130615, 4.073129653930664, 3.347909688949585, 2.1294987201690674, 3.1730141639709473, 3.1268818378448486, 2.7368710041046143, 3.312624454498291, 2.591076612472534, 2.6305456161499023, 3.6804873943328857, 3.214876651763916, 4.2072882652282715, 3.510282516479492, 4.2991509437561035, 2.189208984375, 2.680189847946167, 3.5076427459716797, 4.733257293701172, 4.694076061248779, 3.255465507507324, 2.9686119556427, 4.279423713684082, 2.7126684188842773, 3.3103649616241455, 2.3789100646972656, 3.0469810962677, 2.679654598236084, 3.0809338092803955, 2.597945213317871, 4.042031288146973, 2.137371063232422, 2.5765349864959717, 2.2155985832214355, 3.687119722366333, 2.8792805671691895, 2.71317195892334, 3.4769656658172607, 3.7349693775177, 4.268000602722168, 2.689291000366211, 3.197622299194336, 3.1963798999786377, 2.7187981605529785, 2.9449379444122314, 2.4139692783355713, 2.605560302734375, 3.669720411300659, 3.937692403793335, 2.488676071166992, 2.895840883255005, 2.622363328933716, 2.7854301929473877, 4.2792744636535645, 3.1294357776641846, 3.3205361366271973, 3.3984286785125732, 1.8311538696289062, 3.9047470092773438, 2.9876925945281982, 3.4324939250946045, 3.1923656463623047, 2.7094714641571045, 2.100713014602661, 3.236121416091919, 2.9376604557037354, 2.6396617889404297, 3.0684115886688232, 2.538689136505127, 3.115421772003174, 2.353511095046997, 3.251248598098755, 2.8184540271759033, 2.6549365520477295, 3.100041389465332, 2.9298095703125, 4.173190593719482, 2.651486873626709, 4.087569713592529, 2.6555557250976562, 61.1881217956543, 144.57373046875, 666.857666015625, 160.97792053222656, 63.69831085205078, 104.19107055664062, 120.11503601074219, 327.83984375, 513.9585571289062, 192.3201141357422, 167.8686065673828, 112.45150756835938, 156.4375, 167.9298858642578, 275.4495849609375, 46.93549728393555, 105.05236053466797, 442.2242736816406, 480.6334228515625, 560.14013671875, 201.5192108154297, 80.64470672607422, 67.93091583251953, 100.1702880859375, 152.243408203125, 167.0341339111328, 353.544677734375, 217.62066650390625, 240.63519287109375, 234.7987518310547, 73.92354583740234, 73.46052551269531, 121.75497436523438, 245.9151153564453, 261.9471130371094, 166.57582092285156, 424.326904296875, 159.50135803222656, 169.4940948486328, 203.7024688720703, 101.6141357421875, 355.3482666015625, 266.1456604003906, 295.1307373046875, 438.208984375, 90.77544403076172, 249.9755859375, 287.77349853515625, 325.82684326171875, 68.63063049316406, 256.3114013671875, 115.83636474609375, 374.4098205566406, 198.7926483154297, 433.1448974609375, 303.4191589355469, 221.3640594482422, 391.5824279785156, 321.3009033203125, 105.63237762451172, 325.3095703125, 220.14122009277344, 196.0938262939453, 281.6767578125, 212.90391540527344, 68.7628173828125, 195.5469512939453, 131.93731689453125, 117.93562316894531, 73.82282257080078, 330.2784423828125, 263.1878662109375, 135.8817138671875, 313.18359375, 339.37225341796875, 318.439208984375, 167.40834045410156, 385.8876953125, 264.8839111328125, 266.0401611328125, 263.6417236328125, 108.31170654296875, 253.69842529296875, 150.59759521484375, 431.04205322265625, 240.85093688964844, 269.34619140625, 132.32498168945312, 258.9061584472656, 265.1881103515625, 72.53289794921875, 250.9400177001953, 433.7412109375, 134.5384521484375, 682.7396240234375, 190.8793487548828, 113.90538787841797, 262.1318664550781, 467.5111083984375, 242.1755828857422, 309.6304931640625, 133.40553283691406, 155.3623046875, 246.02005004882812, 525.1220703125, 342.4503479003906, 65.27027893066406, 433.9537353515625, 64.26492309570312, 59.16986083984375, 255.7220458984375, 198.69894409179688, 390.460693359375, 138.386962890625, 178.13633728027344, 262.8633117675781, 257.504638671875, 277.1526184082031, 104.25830078125, 71.57325744628906, 47.0740966796875, 524.792236328125, 458.263671875, 377.8265686035156, 181.2959747314453, 391.75201416015625, 43.30780029296875, 210.58172607421875, 202.94189453125, 71.0206298828125, 206.8740997314453, 197.248779296875, 411.38671875, 122.93265533447266, 238.0956268310547, 181.3636474609375, 77.1207275390625, 529.1527709960938, 124.89096069335938, 150.693359375, 149.78634643554688, 259.77740478515625, 525.97216796875, 179.81163024902344, 92.72151947021484, 247.58868408203125, 293.0458984375, 315.32611083984375, 289.0135192871094, 355.2862854003906, 416.3399963378906, 440.3985900878906, 206.20358276367188, 296.6741638183594, 258.9813232421875, 124.46367645263672, 288.6627197265625, 179.36643981933594, 64.2718505859375, 442.0392761230469, 163.6081085205078, 101.2618408203125, 73.54862213134766, 169.3187255859375, 426.70892333984375, 102.17066192626953, 128.2201385498047, 108.1512451171875, 447.2801818847656, 85.98505401611328, 175.673828125, 62.405574798583984, 88.8094711303711, 50.997928619384766, 89.485107421875, 175.89083862304688, 180.33421325683594, 184.01419067382812, 73.94720458984375, 316.42626953125, 366.1552734375, 334.24810791015625, 82.87085723876953, 325.9734802246094, 262.6394958496094, 109.27980041503906, 124.7459945678711, 287.89208984375, 77.4962158203125, 399.9061584472656, 263.7185974121094, 176.5706787109375, 261.0269775390625, 130.10089111328125, 414.23974609375, 311.1629638671875, 212.98594665527344, 80.07022094726562, 162.00015258789062, 85.70021057128906, 232.4189453125, 69.12332916259766, 435.9435729980469, 308.2764892578125, 200.74339294433594, 116.5863037109375, 293.2898864746094, 313.626708984375, 74.71460723876953, 63.69257736206055, 226.0991973876953, 199.4679718017578, 156.3216552734375, 507.1839599609375, 212.8192596435547, 246.40167236328125, 77.3724365234375, 78.73411560058594, 342.49755859375, 121.79925537109375, 219.57774353027344, 184.8136749267578, 73.50385284423828, 191.7870330810547, 109.37759399414062, 90.25164794921875, 304.071533203125, 264.68487548828125, 431.3419494628906, 236.4422607421875, 116.17362213134766, 416.5433349609375, 184.705078125, 272.6497802734375, 149.307373046875, 113.05529022216797, 189.59423828125, 75.98564910888672, 341.2892150878906, 204.7683868408203, 84.78802490234375, 58.401458740234375, 111.95121002197266, 612.78857421875, 58.63331985473633, 506.7467041015625, 271.92498779296875, 159.27972412109375, 243.27452087402344, 242.049560546875, 158.70457458496094, 589.4010009765625, 353.74835205078125, 48.83349609375, 188.4873046875, 360.56781005859375, 80.74646759033203, 247.2097930908203, 118.58161926269531, 250.79812622070312, 95.60655975341797, 216.78826904296875, 244.8353271484375, 314.4211730957031, 233.5155487060547, 160.402099609375, 120.35165405273438, 326.5423583984375, 142.04971313476562, 165.63265991210938, 295.288818359375, 432.1232604980469, 412.3976135253906, 475.7726135253906, 356.005615234375, 144.85792541503906, 132.49075317382812, 303.37164306640625, 447.669921875, 303.2550964355469, 48.702762603759766, 89.27951049804688, 319.2672119140625, 208.23870849609375, 320.1826171875, 55.50213623046875, 302.5783386230469, 211.90098571777344, 266.1951599121094, 177.9430694580078, 153.90899658203125, 236.389892578125, 129.17247009277344, 304.8015441894531, 165.9637451171875, 335.22662353515625, 308.1676330566406, 163.6610870361328, 59.1177978515625, 442.6431884765625, 2.823531150817871, 4.1109795570373535, 2.264521598815918, 2.887150764465332, 1.807697057723999, 3.620344877243042, 2.993212938308716, 2.18742036819458, 3.600752830505371, 2.159850835800171, 1.5828684568405151, 3.8096401691436768, 2.653735399246216, 2.1110851764678955, 3.53378963470459, 2.737858772277832, 3.1121819019317627, 2.675471067428589, 2.9080309867858887, 3.548647880554199, 2.208813428878784, 3.6749913692474365, 2.0525219440460205, 3.1877832412719727, 3.0669426918029785, 2.876180648803711, 2.1565794944763184, 3.248009204864502, 2.649970293045044, 2.8808562755584717, 3.269407272338867, 2.1221492290496826, 3.718034505844116, 1.9324525594711304, 3.023022413253784, 2.4835333824157715, 2.2930290699005127, 2.897339105606079, 3.312596559524536, 1.859139323234558, 2.7143144607543945, 4.163307189941406, 3.2269084453582764, 1.9479645490646362, 2.882331132888794, 2.0521233081817627, 1.4020376205444336, 2.0978899002075195, 2.6021203994750977, 2.786242723464966, 2.672809600830078, 2.945788621902466, 4.632170677185059, 3.1866867542266846, 2.684535503387451, 2.154475212097168, 2.595662832260132, 2.7046642303466797, 1.6842550039291382, 2.8399159908294678, 3.429649591445923, 2.340764045715332, 3.9893271923065186, 1.5603569746017456, 2.2472028732299805, 1.9583100080490112, 3.111218214035034, 2.1980090141296387, 3.5549633502960205, 1.2842987775802612, 2.750309467315674, 3.392889976501465, 1.8981364965438843, 2.867981433868408, 2.8498034477233887, 2.284514904022217, 3.0881199836730957, 2.041213035583496, 2.8215456008911133, 4.482089996337891, 2.6678380966186523, 2.4328906536102295, 2.801563024520874, 3.7064788341522217, 3.057939291000366, 2.3323845863342285, 2.2183749675750732, 2.1514275074005127, 2.5402615070343018, 3.2520573139190674, 2.229037284851074, 2.887397050857544, 2.282231330871582, 2.7755284309387207, 3.975592613220215, 3.120685338973999, 2.8815038204193115, 2.289881467819214, 2.1420164108276367, 2.883915901184082, 1.803725242614746, 2.078437566757202, 1.9959897994995117, 3.4161159992218018, 3.441697359085083, 1.6069304943084717, 1.7558867931365967, 3.3145434856414795, 1.8849915266036987, 3.367070198059082, 3.347895622253418, 2.6848113536834717, 2.556962013244629, 2.6566076278686523, 2.207118272781372, 3.1955249309539795, 2.5351996421813965, 2.704310178756714, 2.265610694885254, 1.739863395690918, 2.0622611045837402, 3.4692089557647705, 3.018145799636841, 3.0306572914123535, 2.662785530090332, 1.637929081916809, 2.401937246322632, 4.097123146057129, 3.759768486022949, 1.9904245138168335, 2.1051673889160156, 2.2085866928100586, 2.262843132019043, 2.4800124168395996, 2.1435348987579346, 2.343806028366089, 2.191323757171631, 2.92950439453125, 3.14727520942688, 2.1763439178466797, 2.6308979988098145, 2.6969707012176514, 4.128624439239502, 2.1987905502319336, 2.986720561981201, 2.6402063369750977, 2.761561632156372, 1.7887734174728394, 3.6159145832061768, 3.162810802459717, 2.2167656421661377, 3.074415922164917, 2.5523109436035156, 2.5298967361450195, 1.9951467514038086, 2.6775619983673096, 2.408053398132324, 2.4760425090789795, 2.344527244567871, 3.075211763381958, 1.9380391836166382, 1.827362298965454, 1.8414124250411987, 3.1172893047332764, 1.8977113962173462, 2.4489424228668213, 3.0710246562957764, 2.785010576248169, 2.6776421070098877, 2.2075324058532715, 2.4166595935821533, 2.8574020862579346, 4.262824535369873, 3.056628704071045, 2.56290602684021, 2.6885061264038086, 2.076308488845825, 3.3217363357543945, 2.792367458343506, 2.160273551940918, 1.4792031049728394, 2.6890411376953125, 3.397226572036743, 3.8815488815307617, 1.6065855026245117, 1.7678720951080322, 2.746441602706909, 3.0534417629241943, 2.8370258808135986, 1.9519011974334717, 1.5763839483261108, 2.567227840423584, 3.6300182342529297, 3.8259880542755127, 2.4496490955352783, 3.6025402545928955, 2.2403249740600586, 2.6288483142852783, 1.9954137802124023, 3.3069145679473877, 3.70328426361084, 2.585466146469116, 1.6221894025802612, 3.5067286491394043, 3.5261178016662598, 2.749434232711792, 2.642106294631958, 1.5109548568725586, 3.7762839794158936, 2.5417985916137695, 2.0673837661743164, 2.0237200260162354, 1.6671003103256226, 2.1111536026000977, 2.5559747219085693, 1.4893522262573242, 3.043426752090454, 2.1577329635620117, 3.4512746334075928, 2.2145681381225586, 2.0532827377319336, 1.920069694519043, 2.8138701915740967, 1.2899314165115356, 2.664660692214966, 3.908615827560425, 1.7882798910140991, 4.043759822845459, 4.314635276794434, 3.460826873779297, 1.7246778011322021, 4.48197603225708, 3.92696213722229, 4.1794352531433105, 3.3850927352905273, 1.5688549280166626, 1.3491371870040894, 1.8886996507644653, 2.6792047023773193, 1.871479868888855, 2.450974702835083, 3.2844200134277344, 2.335186004638672, 3.0254650115966797, 1.9885892868041992, 1.5444881916046143, 2.086453437805176, 3.2770233154296875, 3.0071823596954346, 2.899733304977417, 4.159453868865967, 1.72358238697052, 4.296710014343262, 3.993105888366699, 3.6377782821655273, 2.3270864486694336, 3.4406938552856445, 1.7565926313400269, 3.4094724655151367, 2.424884080886841, 3.6685285568237305, 3.868394136428833, 1.9623823165893555, 1.7458665370941162, 1.9870675802230835, 3.857649564743042, 2.6772313117980957, 2.7873735427856445, 2.5051181316375732, 3.0552656650543213, 2.0202739238739014, 1.6183527708053589, 2.5609965324401855, 2.512561559677124, 2.371211290359497, 3.7161192893981934, 1.7067753076553345, 3.8994686603546143, 2.558420419692993, 3.8625152111053467, 2.8826611042022705, 2.486755847930908, 3.2706520557403564, 3.9123942852020264, 1.4019110202789307, 3.3332748413085938, 1.588387370109558, 1.6552648544311523, 2.9385499954223633, 2.5339064598083496, 3.261768102645874, 2.701892614364624, 2.281309127807617, 2.237966537475586, 4.071722507476807, 3.3461363315582275, 1.1975868940353394, 3.0444324016571045, 1.96306312084198, 2.9009110927581787, 0.23726558685302734, 0.2203018069267273, 0.27279090881347656, 0.2692701518535614, 0.21277911961078644, 0.1938377022743225, 0.23417454957962036, 0.26792097091674805, 0.30321645736694336, 0.2150460034608841, 0.22249673306941986, 0.26611632108688354, 0.26842597126960754, 0.2293863296508789, 0.23617833852767944, 0.28327715396881104, 0.22153335809707642, 0.29792362451553345, 0.189325213432312, 0.2398248165845871, 0.1866026222705841, 0.1895657479763031, 0.21891894936561584, 0.21758422255516052, 0.22705000638961792, 0.23020686209201813, 0.2628377377986908, 0.26275646686553955, 0.22454261779785156, 0.26012876629829407, 0.21323350071907043, 0.21764834225177765, 0.24502120912075043, 0.23139628767967224, 0.19090449810028076, 0.2925339341163635, 0.20679664611816406, 0.21361081302165985, 0.24548190832138062, 0.24256420135498047, 0.25085726380348206, 0.23175875842571259, 0.24963611364364624, 0.2900868058204651, 0.25535857677459717, 0.21093133091926575, 0.23520787060260773, 0.2052449733018875, 0.3182269334793091, 0.18826229870319366, 0.19825568795204163, 0.3167620897293091, 0.25221094489097595, 0.23980842530727386, 0.23330457508563995, 0.2906063497066498, 0.2858954668045044, 0.2691101133823395, 0.24786345660686493, 0.3449971675872803, 0.21566782891750336, 0.26482152938842773, 0.3017050623893738, 0.2129766345024109, 0.2270805835723877, 0.2991795539855957, 0.23752546310424805, 0.2655157744884491, 0.240585058927536, 0.2600007951259613, 0.2792864143848419, 0.19738143682479858, 0.29257091879844666, 0.2385237067937851, 0.2861390709877014, 0.24214476346969604, 0.18629823625087738, 0.19591151177883148, 0.26535624265670776, 0.2475358098745346, 0.27200132608413696, 0.24548262357711792, 0.21761099994182587, 0.2714840769767761, 0.28754356503486633, 0.26930081844329834, 0.2527540624141693, 0.19072778522968292, 0.2680375874042511, 0.18895648419857025, 0.2739699184894562, 0.2582647204399109, 0.2467603236436844, 0.24892878532409668, 0.2726265788078308, 0.2755545675754547, 0.2233555167913437, 0.24273806810379028, 0.28937453031539917, 0.2509530186653137, 0.26256367564201355, 0.2344372570514679, 0.29727911949157715, 0.29275715351104736, 0.178834468126297, 0.2442670315504074, 0.2986542582511902, 0.20895551145076752, 0.23183605074882507, 0.2425193041563034, 0.29987066984176636, 0.24254639446735382, 0.2265627682209015, 0.22509732842445374, 0.2053796499967575, 0.2652326822280884, 0.24329181015491486, 0.22773200273513794, 0.3200431764125824, 0.24111376702785492, 0.2663690447807312, 0.2116103321313858, 0.26226940751075745, 0.30661898851394653, 0.2006026953458786, 0.16706618666648865, 0.3187960088253021, 0.22382286190986633, 0.3133031129837036, 0.25091901421546936, 0.317006379365921, 0.3066389262676239, 0.27986401319503784, 0.22140441834926605, 0.21635191142559052, 0.27104198932647705, 0.1898220032453537, 0.305669903755188, 0.1916465312242508, 0.309177041053772, 0.27521786093711853, 0.28395989537239075, 0.299266517162323, 0.2663523256778717, 0.2849395275115967, 0.286932110786438, 0.1814904510974884, 0.24452777206897736, 0.26582571864128113, 0.23366214334964752, 0.3113233745098114, 0.2520414888858795, 0.3447040617465973, 0.2418801635503769, 0.26422634720802307, 0.2923855483531952, 0.23445743322372437, 0.2242240160703659, 0.25957033038139343, 0.3021239638328552, 0.21872909367084503, 0.197244331240654, 0.21362729370594025, 0.21038849651813507, 0.29031410813331604, 0.238735631108284, 0.3226156234741211, 0.2558472454547882, 0.1946917325258255, 0.2700047194957733, 0.25464966893196106, 0.30405595898628235, 0.2228533923625946, 0.25620901584625244, 0.24160236120224, 0.2687015235424042, 0.27152225375175476, 0.27245983481407166, 0.23705653846263885, 0.1925959289073944, 0.2774198055267334, 0.28876832127571106, 0.24179938435554504, 0.2884714603424072, 0.2167123407125473, 0.28149154782295227, 0.2288714498281479, 0.2324994057416916, 0.2815954387187958, 0.22151832282543182, 0.23045921325683594, 0.26253360509872437, 0.23471644520759583, 0.24006886780261993, 0.17914271354675293, 0.29036277532577515, 0.20801478624343872, 0.22627335786819458, 0.27327603101730347, 0.21409793198108673, 0.2319764345884323, 0.23317767679691315, 0.21707673370838165, 0.23788414895534515, 0.3270820677280426, 0.19076602160930634, 0.2574600875377655, 0.2459663301706314, 0.2744143009185791, 0.2403550148010254, 0.235025092959404, 0.19739818572998047, 0.3227483928203583, 0.18154139816761017, 0.22130784392356873, 0.255700945854187, 0.24068768322467804, 0.24700385332107544, 0.23869752883911133, 0.2510709762573242, 0.2313435673713684, 0.2527257204055786, 0.2075677067041397, 0.27541351318359375, 0.29338711500167847, 0.28688597679138184, 0.2517399787902832, 0.22917141020298004, 0.2577503025531769, 0.23285505175590515, 0.2934793531894684, 0.22608958184719086, 0.3241167664527893, 0.2529798150062561, 0.28032946586608887, 0.18449704349040985, 0.21991214156150818, 0.2543538808822632, 0.19367678463459015, 0.25065264105796814, 0.2063843160867691, 0.18049100041389465, 0.25692301988601685, 0.23630152642726898, 0.2736895680427551, 0.2294955998659134, 0.22423288226127625, 0.240278422832489, 0.21751555800437927, 0.2326773852109909, 0.20749816298484802, 0.2891412675380707, 0.29146647453308105, 0.29234057664871216, 0.24640563130378723, 0.23306424915790558, 0.3292541801929474, 0.30551642179489136, 0.2559603154659271, 0.2567906975746155, 0.19587306678295135, 0.24784709513187408, 0.2470928579568863, 0.22415347397327423, 0.25060534477233887, 0.2595617473125458, 0.2034885734319687, 0.2827170193195343, 0.22658395767211914, 0.2899094820022583, 0.20683757960796356, 0.25927644968032837, 0.2797548770904541, 0.27052798867225647, 0.25015318393707275, 0.22310347855091095, 0.32668107748031616, 0.285444974899292, 0.296215295791626, 0.2536941468715668, 0.2809191048145294, 0.261517733335495, 0.2609843611717224, 0.24876220524311066, 0.26631155610084534, 0.25585421919822693, 0.24011185765266418, 0.29980823397636414, 0.2102580964565277, 0.3052535057067871, 0.2577512860298157, 0.20915068686008453, 0.2860017418861389, 0.25537824630737305, 0.31417736411094666, 0.3098882734775543, 0.2308453768491745, 0.2039281725883484, 0.196316197514534, 0.26160144805908203, 2.9334137439727783, 2.422424554824829, 3.5120129585266113, 2.478327751159668, 2.8094170093536377, 3.1044704914093018, 2.8975682258605957, 3.1802494525909424, 2.5243046283721924, 1.6677465438842773, 2.8138248920440674, 4.370804786682129, 3.710794687271118, 3.1570165157318115, 3.1947996616363525, 3.5847997665405273, 2.3463799953460693, 4.3643999099731445, 2.8159592151641846, 2.196976900100708, 3.137714147567749, 4.409607887268066, 4.968752384185791, 2.5403854846954346, 3.021986722946167, 2.958203077316284, 3.3762505054473877, 3.08189058303833, 2.2497329711914062, 2.2530179023742676, 3.138370990753174, 3.7512593269348145, 3.522372245788574, 3.8298540115356445, 4.974023818969727, 3.6656060218811035, 2.830692768096924, 2.689479351043701, 3.3630740642547607, 3.055415391921997, 4.723186492919922, 3.1580541133880615, 4.174957752227783, 2.436009407043457, 2.9870731830596924, 3.472172260284424, 2.9964568614959717, 3.130727767944336, 3.659731864929199, 2.7873642444610596, 2.924504280090332, 2.7220001220703125, 3.3200786113739014, 2.544548988342285, 3.1134092807769775, 2.97220778465271, 2.761556625366211, 4.02186918258667, 3.244540214538574, 2.558586597442627, 2.2689359188079834, 4.26462984085083, 2.8330605030059814, 2.0113415718078613, 2.683054208755493, 4.051513671875, 3.2888636589050293, 4.630000591278076, 3.5599560737609863, 3.731274366378784, 2.6865899562835693, 4.150669574737549, 3.934246778488159, 3.3588008880615234, 2.640275716781616, 3.12589430809021, 3.1008403301239014, 2.4983420372009277, 2.3087098598480225, 1.8597253561019897, 3.48382568359375, 3.6623425483703613, 2.2879717350006104, 3.3688278198242188, 4.004421234130859, 2.216282844543457, 2.8091156482696533, 2.711292028427124, 2.3493168354034424, 2.713611364364624, 3.552180767059326, 2.5473954677581787, 2.1382741928100586, 2.6030802726745605, 4.156296253204346, 2.9769420623779297, 4.737621784210205, 2.6245665550231934, 3.3161492347717285, 3.7501819133758545, 1.9022234678268433, 2.589634895324707, 3.684957504272461, 2.2969207763671875, 2.7772011756896973, 1.9023195505142212, 3.7721779346466064, 2.650649309158325, 3.930192232131958, 3.268573522567749, 3.013538122177124, 2.171382188796997, 4.257279396057129, 3.4060685634613037, 1.8583942651748657, 2.2702856063842773, 2.7514970302581787, 3.0509190559387207, 2.309749126434326, 4.911454200744629, 3.4547741413116455, 2.378775119781494, 3.2735466957092285, 2.653027296066284, 3.3544762134552, 4.2910990715026855, 4.691133975982666, 3.798222541809082, 3.084108829498291, 3.5809872150421143, 3.9734067916870117, 4.469376564025879, 2.711378812789917, 2.242037773132324, 3.1868011951446533, 2.856400728225708, 3.5680928230285645, 4.503056049346924, 2.5478808879852295, 4.630712032318115, 2.938930034637451, 4.825109004974365, 3.8594865798950195, 2.0504159927368164, 1.6938021183013916, 3.665109395980835, 3.080521821975708, 3.399308443069458, 3.5822081565856934, 2.073458671569824, 3.279979705810547, 3.58968186378479, 3.7618560791015625, 2.9164223670959473, 4.4039306640625, 3.5375916957855225, 2.7417824268341064, 2.3845443725585938, 3.16092848777771, 2.5181708335876465, 2.8788979053497314, 2.3770766258239746, 4.710484981536865, 1.9503275156021118, 2.3268353939056396, 2.1359431743621826, 3.018388032913208, 3.096806526184082, 2.8507866859436035, 4.205602645874023, 2.211968421936035, 4.046262741088867, 3.028630495071411, 2.7661962509155273, 2.271557331085205, 2.483682155609131, 3.5585503578186035, 3.416517972946167, 2.7209718227386475, 4.6775617599487305, 2.9909508228302, 3.72412109375, 3.560551643371582, 3.069195508956909, 2.8867721557617188, 2.556206703186035, 3.459606885910034, 3.7079920768737793, 3.199895143508911, 4.969385147094727, 3.0874481201171875, 2.8834521770477295, 3.174081563949585, 1.9601974487304688, 3.060319662094116, 2.892040252685547, 2.1385791301727295, 3.32830548286438, 4.463581562042236, 3.5749664306640625, 2.183120012283325, 2.1924896240234375, 2.5071792602539062, 2.9136388301849365, 3.5202431678771973, 3.26278018951416, 3.823307514190674, 2.338845729827881, 2.741892099380493, 3.7371861934661865, 3.3813183307647705, 2.6255106925964355, 2.4261584281921387, 2.454771041870117, 3.979706287384033, 2.942009449005127, 3.8425753116607666, 2.7144250869750977, 3.532691240310669, 3.4321975708007812, 2.8264763355255127, 2.8360350131988525, 2.5736706256866455, 2.468254566192627, 3.0307793617248535, 2.775299072265625, 2.422070026397705, 2.5377213954925537, 2.769375801086426, 2.3492987155914307, 2.7929279804229736, 3.7386474609375, 2.1010055541992188, 2.070204496383667, 3.9297759532928467, 4.681390762329102, 3.37420654296875, 3.2560620307922363, 2.1847620010375977, 3.4158875942230225, 2.3187878131866455, 2.820636510848999, 3.0307421684265137, 3.241445779800415, 3.6551787853240967, 4.522062301635742, 3.841890811920166, 3.1028695106506348, 2.1634650230407715, 3.704899787902832, 3.6557328701019287, 2.8223400115966797, 3.4163224697113037, 3.438539981842041, 3.3595409393310547, 2.2947821617126465, 2.7431845664978027, 1.908022165298462, 4.1424689292907715, 2.2535324096679688, 2.4616692066192627, 2.802389144897461, 3.8130297660827637, 3.8702633380889893, 4.225861549377441, 3.111335039138794, 3.9157779216766357, 2.643455743789673, 3.1841447353363037, 2.188387632369995, 3.237480640411377, 2.595921516418457, 3.601016044616699, 3.102294921875, 3.2372350692749023, 2.362861156463623, 3.1889748573303223, 1.8506906032562256, 3.0387794971466064, 3.6158459186553955, 2.7239444255828857, 2.7385623455047607, 3.409792900085449, 3.051147937774658, 2.891674041748047, 3.1796252727508545, 2.174370050430298, 3.9407641887664795, 3.2825512886047363, 1.8543049097061157, 4.9528021812438965, 2.3768184185028076, 2.352106809616089, 3.5276482105255127, 3.1954410076141357, 2.6048970222473145, 1.7337124347686768, 2.4916505813598633, 2.2245917320251465, 2.6326310634613037, 67.4879150390625, 144.35935974121094, 309.3211669921875, 270.8038330078125, 315.96356201171875, 170.3806610107422, 204.16946411132812, 481.6158752441406, 337.8611755371094, 201.79161071777344, 397.7235412597656, 283.8770751953125, 182.7200927734375, 413.1319580078125, 243.2996826171875, 451.2159729003906, 274.1445617675781, 509.19921875, 311.6607666015625, 151.0872802734375, 75.47406005859375, 169.2919921875, 391.18255615234375, 418.3011474609375, 307.4964904785156, 600.366455078125, 361.4264221191406, 57.993953704833984, 335.62896728515625, 97.47081756591797, 332.8631286621094, 313.3773193359375, 144.86126708984375, 180.5113067626953, 169.1169891357422, 135.0172119140625, 522.4169311523438, 627.10888671875, 562.0684204101562, 126.63558197021484, 69.61493682861328, 258.79656982421875, 192.35487365722656, 481.1546630859375, 63.259521484375, 159.6328125, 314.616943359375, 468.1239318847656, 123.75653839111328, 88.94764709472656, 408.2394104003906, 104.42716217041016, 88.31987762451172, 407.5824890136719, 249.08018493652344, 249.6742706298828, 402.74371337890625, 215.8714599609375, 70.86245727539062, 253.60459899902344, 379.3544921875, 306.0755920410156, 189.67724609375, 350.4471130371094, 245.9272003173828, 97.28234100341797, 126.67791748046875, 90.38822937011719, 160.234130859375, 108.90245819091797, 128.19573974609375, 372.9732666015625, 286.1486511230469, 469.81201171875, 434.076904296875, 301.22943115234375, 135.99514770507812, 406.6856994628906, 220.1581268310547, 96.8860855102539, 545.404052734375, 107.76461029052734, 558.0850830078125, 371.21826171875, 307.6058044433594, 713.2301635742188, 302.3521728515625, 222.45811462402344, 65.27694702148438, 53.99432373046875, 306.2392578125, 446.815185546875, 562.74755859375, 56.20068359375, 81.76909637451172, 298.65386962890625, 93.489990234375, 294.58355712890625, 320.3191833496094, 440.6978759765625, 127.39824676513672, 137.54766845703125, 68.077392578125, 75.74576568603516, 327.90423583984375, 42.48701477050781, 168.9296875, 257.364013671875, 387.6885986328125, 188.7708282470703, 128.946044921875, 156.40724182128906, 202.11441040039062, 463.66943359375, 140.509033203125, 187.15530395507812, 161.92567443847656, 220.01918029785156, 293.65576171875, 386.9015197753906, 218.0742950439453, 285.167724609375, 283.0928955078125, 109.4163818359375, 61.9794921875, 215.40257263183594, 208.51377868652344, 195.1151580810547, 514.92138671875, 348.6148376464844, 69.66365051269531, 157.6371612548828, 482.4742736816406, 94.29907989501953, 447.1047058105469, 409.10296630859375, 274.9820251464844, 110.59553527832031, 279.3111572265625, 355.25726318359375, 113.60746002197266, 91.79872131347656, 203.751708984375, 287.849609375, 183.3336639404297, 86.95672607421875, 432.0931396484375, 196.3203887939453, 148.26226806640625, 357.9705810546875, 293.4515380859375, 270.0008544921875, 326.0302734375, 393.7626953125, 313.58062744140625, 130.60235595703125, 227.25958251953125, 330.1846008300781, 200.21774291992188, 228.384765625, 368.9717102050781, 353.1791687011719, 178.51904296875, 427.4025573730469, 90.80693817138672, 225.66531372070312, 206.63134765625, 463.2857666015625, 316.32135009765625, 64.60629272460938, 306.426513671875, 557.255615234375, 263.0499572753906, 194.73377990722656, 352.3420104980469, 285.1205139160156, 442.6393127441406, 270.0741271972656, 60.485408782958984, 124.49175262451172, 209.50799560546875, 275.44287109375, 540.139892578125, 188.695068359375, 164.80419921875, 161.62510681152344, 123.2626724243164, 122.29995727539062, 190.9779815673828, 126.594970703125, 125.29663848876953, 234.97268676757812, 261.13763427734375, 317.66357421875, 104.8422622680664, 182.13018798828125, 157.2933807373047, 279.4278869628906, 111.34575653076172, 57.4289436340332, 379.0087890625, 171.2183380126953, 183.7875518798828, 383.55755615234375, 212.99920654296875, 51.773895263671875, 154.20277404785156, 428.9676818847656, 267.7345275878906, 83.59954833984375, 108.15572357177734, 163.05471801757812, 83.66116333007812, 119.8640365600586, 135.496826171875, 104.72323608398438, 491.3353271484375, 207.03433227539062, 209.76524353027344, 85.92510223388672, 510.5499572753906, 412.81158447265625, 147.23582458496094, 207.11883544921875, 231.0564727783203, 385.072265625, 305.8601989746094, 213.7020721435547, 137.0204315185547, 167.45947265625, 221.1513671875, 145.4647216796875, 342.5851135253906, 82.1595458984375, 74.82373046875, 168.96299743652344, 132.88525390625, 200.29710388183594, 166.74273681640625, 356.5086669921875, 94.8818359375, 210.8471221923828, 137.814697265625, 416.9820861816406, 361.79150390625, 226.12738037109375, 461.38800048828125, 211.6689453125, 145.45880126953125, 139.24163818359375, 156.7590789794922, 62.818153381347656, 220.86984252929688, 108.02658081054688, 205.44549560546875, 108.68708801269531, 57.171875, 109.44170379638672, 322.0740661621094, 223.7572021484375, 378.8226623535156, 215.5546112060547, 218.7474365234375, 98.32684326171875, 77.85283660888672, 129.003173828125, 135.60015869140625, 124.84964752197266, 180.9654083251953, 59.43817138671875, 173.59146118164062, 158.41400146484375, 161.68984985351562, 453.6859130859375, 253.78759765625, 359.830810546875, 162.10845947265625, 316.26953125, 90.67864990234375, 384.4703369140625, 239.241943359375, 502.5763854980469, 223.1863250732422, 422.4586181640625, 76.82666015625, 312.45013427734375, 257.51806640625, 287.7922058105469, 53.48463821411133, 558.0299072265625, 361.9715270996094, 99.41860961914062, 214.97154235839844, 273.5024108886719, 179.9268341064453, 241.2555389404297, 453.005615234375, 77.39601135253906, 179.572021484375, 201.5839080810547, 4.222437858581543, 3.8123557567596436, 2.008143424987793, 3.114335298538208, 3.289332151412964, 2.2907495498657227, 2.8417882919311523, 2.27841854095459, 2.6697723865509033, 2.538604736328125, 1.9595626592636108, 2.3103065490722656, 1.867332100868225, 2.5905563831329346, 1.7439736127853394, 3.816012382507324, 1.881020426750183, 2.9851326942443848, 1.5393344163894653, 2.8310546875, 2.6577093601226807, 3.9203343391418457, 1.6051597595214844, 2.8573858737945557, 4.301943778991699, 2.3720693588256836, 3.5393168926239014, 4.296500205993652, 2.91015625, 2.1623048782348633, 2.165066719055176, 3.5887022018432617, 2.7534990310668945, 1.5160000324249268, 2.949540376663208, 3.163348436355591, 1.7137043476104736, 3.575650453567505, 3.2476983070373535, 3.731400728225708, 2.7618460655212402, 2.861900806427002, 2.61112117767334, 2.7139458656311035, 2.849034309387207, 1.7908544540405273, 3.4805800914764404, 3.838373899459839, 3.186124801635742, 2.27854061126709, 3.7636642456054688, 1.9815959930419922, 1.7408781051635742, 2.0109148025512695, 1.9735153913497925, 2.7678704261779785, 2.961597204208374, 2.722015857696533, 2.493189811706543, 2.1981558799743652, 2.634648323059082, 3.213658332824707, 2.8180224895477295, 1.7901443243026733, 2.1653168201446533, 3.3286592960357666, 2.140061855316162, 2.6207008361816406, 2.905982494354248, 2.457167625427246, 3.8383989334106445, 2.49318790435791, 1.9911298751831055, 1.9286015033721924, 1.934153437614441, 2.691333055496216, 2.5487618446350098, 3.471611976623535, 2.167490243911743, 3.5536744594573975, 3.165616273880005, 1.8514324426651, 3.3457517623901367, 2.2175509929656982, 2.632564067840576, 2.6649487018585205, 2.204047441482544, 3.0013768672943115, 2.3956634998321533, 2.1866888999938965, 2.5622076988220215, 2.4665367603302, 2.0117645263671875, 2.9858829975128174, 2.625729560852051, 2.7369906902313232, 2.176652431488037, 3.186458110809326, 2.71928334236145, 1.687325358390808, 2.7125842571258545, 3.0131943225860596, 1.8386309146881104, 1.8221572637557983, 3.1862809658050537, 3.275179862976074, 3.7295610904693604, 1.9386147260665894, 2.1208696365356445, 2.5888280868530273, 3.3511297702789307, 2.5783092975616455, 2.6282243728637695, 2.2388298511505127, 2.025179862976074, 1.8224002122879028, 2.0717573165893555, 2.0668554306030273, 2.66152286529541, 2.3765878677368164, 3.9651365280151367, 2.222710132598877, 1.5366926193237305, 2.0802664756774902, 3.6855742931365967, 4.018637657165527, 1.559876561164856, 2.1405789852142334, 2.962681293487549, 2.395798683166504, 1.9079952239990234, 2.52834415435791, 1.4348915815353394, 3.581568479537964, 2.307302474975586, 1.6572751998901367, 3.6676206588745117, 1.987563133239746, 1.6445097923278809, 2.936776876449585, 2.2640886306762695, 2.3516054153442383, 2.641106605529785, 2.073256254196167, 2.2233920097351074, 3.868068218231201, 4.299510955810547, 1.7539209127426147, 2.8158066272735596, 3.080817222595215, 2.7232091426849365, 1.9928292036056519, 2.5987439155578613, 3.2197446823120117, 3.1319808959960938, 2.3599870204925537, 1.7429773807525635, 3.707320213317871, 3.001631021499634, 1.5739067792892456, 3.0310754776000977, 2.42073917388916, 3.199662923812866, 3.0590035915374756, 2.57231068611145, 2.82840633392334, 1.7022618055343628, 2.3935651779174805, 1.8539915084838867, 2.1570444107055664, 1.765741229057312, 2.707686185836792, 2.843581438064575, 2.7121212482452393, 2.263188362121582, 1.644728660583496, 1.9256943464279175, 2.7907938957214355, 4.245339393615723, 2.1373703479766846, 3.5535876750946045, 2.817838668823242, 3.122929573059082, 2.4104249477386475, 3.754415273666382, 3.226442813873291, 1.7720670700073242, 2.7631585597991943, 2.8036930561065674, 2.662167549133301, 4.15928316116333, 1.8498677015304565, 2.8995721340179443, 3.564100503921509, 1.917397379875183, 2.5562028884887695, 1.7503026723861694, 1.5294235944747925, 2.052454710006714, 2.185991048812866, 1.913630485534668, 4.1286516189575195, 2.68808650970459, 2.403775691986084, 2.356656789779663, 3.3825182914733887, 3.35247540473938, 2.387791633605957, 3.035598039627075, 2.9973669052124023, 3.8226804733276367, 2.215446710586548, 1.8921728134155273, 1.9957380294799805, 2.464688777923584, 2.749441146850586, 3.005202054977417, 3.951663017272949, 2.2560300827026367, 3.434688091278076, 3.0326929092407227, 2.547661781311035, 1.955367088317871, 1.9424484968185425, 2.1774821281433105, 2.390766143798828, 2.6722099781036377, 3.520676851272583, 2.213061571121216, 2.3619396686553955, 2.9348156452178955, 1.6844321489334106, 2.4235353469848633, 3.2534332275390625, 2.936175584793091, 1.6111516952514648, 2.1450042724609375, 2.5454301834106445, 2.924730062484741, 3.4502782821655273, 3.0455048084259033, 1.7979668378829956, 2.4137537479400635, 3.837662935256958, 2.22489070892334, 3.0607216358184814, 3.4319818019866943, 1.9497421979904175, 2.2800493240356445, 2.838285207748413, 2.5835583209991455, 3.056060791015625, 3.3473851680755615, 3.019152879714966, 2.321967124938965, 2.5499143600463867, 1.8237961530685425, 2.1144824028015137, 2.018425941467285, 2.7187511920928955, 1.9766933917999268, 3.46817684173584, 2.6288440227508545, 2.8710010051727295, 2.8934326171875, 2.3807530403137207, 2.0955536365509033, 2.9713966846466064, 2.5727648735046387, 2.221238136291504, 2.3439455032348633, 2.992785692214966, 1.592610478401184, 1.4756628274917603, 2.2958993911743164, 2.7133703231811523, 2.2761011123657227, 3.550605058670044, 2.7602341175079346, 4.138668537139893, 2.622159957885742, 2.5737438201904297, 2.334345817565918, 2.419623374938965, 3.5671586990356445, 2.938944101333618, 2.4354233741760254, 3.045198678970337, 2.95231032371521, 1.9333144426345825, 2.9831783771514893, 2.8573808670043945, 3.767460823059082, 2.9155778884887695, 1.6851662397384644, 1.7962217330932617, 3.860934257507324, 3.578812837600708, 2.487060070037842, 3.8944201469421387, 0.23065753281116486, 0.21439309418201447, 0.2401614934206009, 0.26795312762260437, 0.26415780186653137, 0.25139424204826355, 0.2548026740550995, 0.2106609046459198, 0.22805705666542053, 0.2935405373573303, 0.23493163287639618, 0.2575075328350067, 0.24206964671611786, 0.29666033387184143, 0.2010771930217743, 0.25243765115737915, 0.29794275760650635, 0.262756884098053, 0.2661133110523224, 0.29444974660873413, 0.2547934949398041, 0.23809102177619934, 0.3042413592338562, 0.2849731147289276, 0.26991140842437744, 0.2814100682735443, 0.2666017413139343, 0.22288669645786285, 0.23668956756591797, 0.31030911207199097, 0.26230958104133606, 0.2542780637741089, 0.2624906599521637, 0.24759458005428314, 0.2802523076534271, 0.25810226798057556, 0.2782815992832184, 0.24888864159584045, 0.24684131145477295, 0.27114638686180115, 0.27611416578292847, 0.217202290892601, 0.25169527530670166, 0.2325192540884018, 0.25624385476112366, 0.27607452869415283, 0.2150331288576126, 0.2351410686969757, 0.28916269540786743, 0.22299787402153015, 0.18135301768779755, 0.2241126149892807, 0.2443431168794632, 0.21158115565776825, 0.2008737325668335, 0.2642846703529358, 0.20423412322998047, 0.24686305224895477, 0.22975099086761475, 0.208072692155838, 0.20878097414970398, 0.26916074752807617, 0.26330772042274475, 0.2189178764820099, 0.2705944776535034, 0.24404676258563995, 0.27589088678359985, 0.23259980976581573, 0.2407272607088089, 0.24989688396453857, 0.33339205384254456, 0.2836031913757324, 0.20746755599975586, 0.1932072639465332, 0.22900332510471344, 0.2165549397468567, 0.2694106996059418, 0.2599765658378601, 0.21171055734157562, 0.2998836040496826, 0.3074985444545746, 0.2701316773891449, 0.2461402267217636, 0.24769505858421326, 0.28251883387565613, 0.21408489346504211, 0.24148906767368317, 0.16693004965782166, 0.28821471333503723, 0.3005928099155426, 0.31486988067626953, 0.1992284208536148, 0.2439795583486557, 0.27273857593536377, 0.2708609402179718, 0.2354341298341751, 0.15657776594161987, 0.24093961715698242, 0.291061133146286, 0.23536185920238495, 0.2312908172607422, 0.3214072287082672, 0.256467342376709, 0.24918422102928162, 0.24134568870067596, 0.2553815543651581, 0.24407394230365753, 0.21326278150081635, 0.26019057631492615, 0.2162991315126419, 0.230423241853714, 0.2569464147090912, 0.2656764090061188, 0.1998501867055893, 0.24872829020023346, 0.22443459928035736, 0.30071619153022766, 0.20598959922790527, 0.2234363853931427, 0.2698906362056732, 0.24361276626586914, 0.23006916046142578, 0.26840612292289734, 0.2010406255722046, 0.2738407850265503, 0.28867700695991516, 0.2281980812549591, 0.2621816396713257, 0.23605689406394958, 0.2282591164112091, 0.2125028818845749, 0.3093903362751007, 0.2995879352092743, 0.19509084522724152, 0.2905065715312958, 0.2322528064250946, 0.25496965646743774, 0.24709796905517578, 0.21592755615711212, 0.26881808042526245, 0.24635916948318481, 0.2327364683151245, 0.2595977485179901, 0.24679385125637054, 0.20841138064861298, 0.1981053501367569, 0.3005158305168152, 0.23599523305892944, 0.21952170133590698, 0.2700481414794922, 0.2478080689907074, 0.21867255866527557, 0.28363245725631714, 0.2695551812648773, 0.22697703540325165, 0.29644373059272766, 0.22976276278495789, 0.27564847469329834, 0.22087936103343964, 0.22780677676200867, 0.2914960980415344, 0.23407462239265442, 0.2971230745315552, 0.21123045682907104, 0.23564115166664124, 0.2551792562007904, 0.2800542712211609, 0.30005690455436707, 0.25018930435180664, 0.21643462777137756, 0.3381607234477997, 0.26857665181159973, 0.22653409838676453, 0.2656502425670624, 0.26605722308158875, 0.2877979874610901, 0.27299878001213074, 0.24579577147960663, 0.29912757873535156, 0.21354950964450836, 0.2747613787651062, 0.22867463529109955, 0.14322330057621002, 0.2693396210670471, 0.28920799493789673, 0.19897665083408356, 0.26287221908569336, 0.22553949058055878, 0.27422013878822327, 0.21679191291332245, 0.273418128490448, 0.2669837772846222, 0.2795320451259613, 0.20769862830638885, 0.2415895164012909, 0.23174035549163818, 0.2220807671546936, 0.20021945238113403, 0.25974422693252563, 0.2574669122695923, 0.23935168981552124, 0.2727750241756439, 0.17221374809741974, 0.21569888293743134, 0.23410218954086304, 0.24617040157318115, 0.2693452835083008, 0.23110425472259521, 0.21368274092674255, 0.2718898355960846, 0.23108360171318054, 0.25180524587631226, 0.2430625855922699, 0.2798217535018921, 0.1967429369688034, 0.25139567255973816, 0.30566149950027466, 0.26422712206840515, 0.2753673195838928, 0.25464123487472534, 0.21629157662391663, 0.22487832605838776, 0.31133055686950684, 0.24792514741420746, 0.260422021150589, 0.23454701900482178, 0.25874951481819153, 0.28204455971717834, 0.2638942301273346, 0.20969529449939728, 0.18942992389202118, 0.2228022664785385, 0.23197682201862335, 0.27271315455436707, 0.28637510538101196, 0.23529356718063354, 0.2500876486301422, 0.2951492369174957, 0.22113807499408722, 0.20794795453548431, 0.20029602944850922, 0.2869379222393036, 0.27270179986953735, 0.2030494660139084, 0.24981917440891266, 0.2449718415737152, 0.32282155752182007, 0.23556506633758545, 0.27508652210235596, 0.2788042426109314, 0.2398221492767334, 0.275556355714798, 0.19185951352119446, 0.25006550550460815, 0.2083040028810501, 0.14229539036750793, 0.23480041325092316, 0.2959348261356354, 0.1871662437915802, 0.2859177589416504, 0.22144144773483276, 0.30313873291015625, 0.3232881724834442, 0.2558724582195282, 0.21959812939167023, 0.251216858625412, 0.22476908564567566, 0.30679813027381897, 0.29543378949165344, 0.22507186233997345, 0.23644621670246124, 0.2595093548297882, 0.23625262081623077, 0.21517708897590637, 0.22349844872951508, 0.2175006866455078, 0.2367638796567917, 0.21698734164237976, 0.21179503202438354, 0.24131880700588226, 0.265460342168808, 0.2527022957801819, 0.22947199642658234, 0.26090165972709656, 0.2714792490005493, 0.2786683738231659, 0.2384909838438034, 0.30192381143569946, 0.2574270963668823, 0.25570255517959595, 0.1930103302001953, 0.297861784696579, 0.2027396410703659, 0.24402782320976257, 0.2870047688484192, 0.24519602954387665, 0.2585487365722656, 0.24142882227897644, 0.24592585861682892, 0.22467949986457825, 4.150144577026367, 3.0868852138519287, 3.5655763149261475, 2.1416003704071045, 3.6214711666107178, 2.0534374713897705, 3.413658618927002, 3.398597002029419, 2.6576552391052246, 2.8509175777435303, 3.3352062702178955, 3.811486005783081, 3.0425472259521484, 3.3815324306488037, 3.1764252185821533, 3.3108131885528564, 3.4429802894592285, 3.1896913051605225, 2.869999647140503, 3.984403610229492, 3.8124406337738037, 2.6234188079833984, 4.646915912628174, 2.4834036827087402, 3.692967176437378, 4.353157043457031, 3.7608642578125, 2.767962694168091, 3.1031670570373535, 2.262537956237793, 2.1815872192382812, 1.8307256698608398, 3.64211106300354, 3.3020541667938232, 3.105159282684326, 3.9610252380371094, 4.130812168121338, 3.9880363941192627, 2.7167439460754395, 1.9636961221694946, 3.80029296875, 1.9618438482284546, 2.9296627044677734, 3.952763557434082, 2.2783379554748535, 3.70196270942688, 3.0608696937561035, 2.531046152114868, 4.73615837097168, 3.5377349853515625, 2.2414262294769287, 2.902552843093872, 2.1661622524261475, 4.460243225097656, 2.506899118423462, 3.3940234184265137, 3.1608059406280518, 2.403170585632324, 2.040095567703247, 3.5944786071777344, 3.958545446395874, 3.929584264755249, 2.6321001052856445, 2.1680731773376465, 2.9116485118865967, 4.2712178230285645, 3.458757162094116, 2.3363027572631836, 3.3681678771972656, 2.462677001953125, 3.3569741249084473, 2.5704362392425537, 3.417884111404419, 2.4814867973327637, 3.0215229988098145, 3.3309130668640137, 1.9870599508285522, 3.644987106323242, 2.3072521686553955, 3.7458677291870117, 3.309375524520874, 3.5785434246063232, 3.7821896076202393, 1.897394061088562, 5.042893409729004, 3.659825325012207, 3.7661848068237305, 2.7097678184509277, 3.0250725746154785, 3.28996205329895, 4.023237705230713, 5.798499584197998, 3.22183895111084, 2.338514566421509, 2.8372154235839844, 3.3958423137664795, 4.271015644073486, 2.353576183319092, 3.689401388168335, 3.961472749710083, 2.4068925380706787, 3.3947200775146484, 4.0237717628479, 3.517096996307373, 2.253843307495117, 2.32954740524292, 4.438755512237549, 2.1102776527404785, 2.2793350219726562, 3.498624086380005, 3.217012882232666, 4.280463218688965, 4.720062255859375, 3.1496875286102295, 2.4363081455230713, 3.4959163665771484, 2.6494884490966797, 4.394989013671875, 2.4589695930480957, 2.125952959060669, 2.569159507751465, 3.0758018493652344, 2.559436321258545, 4.662043571472168, 2.2805519104003906, 3.111356019973755, 2.184354782104492, 2.660179615020752, 3.6865415573120117, 3.9202091693878174, 2.992215394973755, 3.4076595306396484, 2.466608762741089, 2.6663310527801514, 4.1242780685424805, 2.9682159423828125, 2.9559578895568848, 3.0734703540802, 2.911175489425659, 2.9229495525360107, 2.6276581287384033, 2.720700740814209, 2.583848476409912, 2.51275372505188, 2.6992828845977783, 2.0410804748535156, 3.7540366649627686, 4.5598907470703125, 2.929919481277466, 3.274399995803833, 3.134122848510742, 1.5873521566390991, 2.9730775356292725, 2.409304141998291, 3.407132387161255, 3.4738175868988037, 4.242034912109375, 2.5225236415863037, 3.132380723953247, 3.6971652507781982, 2.4641945362091064, 3.8976380825042725, 2.3217790126800537, 2.616846799850464, 3.1971797943115234, 3.467816114425659, 3.1630053520202637, 3.3708457946777344, 2.4986166954040527, 3.7751529216766357, 1.8949865102767944, 3.7659313678741455, 1.9553591012954712, 4.269325256347656, 2.5056838989257812, 3.6729259490966797, 3.318375825881958, 2.2609047889709473, 3.2494606971740723, 4.304853916168213, 2.450920343399048, 3.1343605518341064, 3.5350072383880615, 3.160475969314575, 3.1890313625335693, 4.806021213531494, 2.820026159286499, 3.0167031288146973, 2.9591875076293945, 1.816752552986145, 3.0928947925567627, 2.934990406036377, 5.0816850662231445, 3.602755069732666, 2.479417562484741, 2.849973678588867, 2.981232166290283, 2.3785829544067383, 2.6531786918640137, 1.8022589683532715, 4.596714496612549, 2.107938766479492, 4.030254364013672, 2.3335020542144775, 2.6792988777160645, 2.8648691177368164, 3.242692232131958, 2.8242199420928955, 5.073978900909424, 4.219452857971191, 2.8322091102600098, 3.0870754718780518, 2.8663430213928223, 2.6387102603912354, 3.1976420879364014, 2.823972702026367, 2.3448681831359863, 3.0546820163726807, 4.251142978668213, 2.2006115913391113, 2.3787264823913574, 4.914557456970215, 4.017412185668945, 3.8210437297821045, 2.450552225112915, 3.3855068683624268, 2.7653591632843018, 3.0871474742889404, 2.4482803344726562, 1.8325719833374023, 3.498844623565674, 5.185647964477539, 1.805112361907959, 4.060663223266602, 3.2343525886535645, 3.1816558837890625, 3.8944079875946045, 2.43125319480896, 2.5901927947998047, 2.810042142868042, 2.9480721950531006, 3.4514665603637695, 3.821587085723877, 2.6825332641601562, 2.7994771003723145, 2.2125601768493652, 3.9057416915893555, 4.238725662231445, 4.733611106872559, 3.8032009601593018, 1.764650583267212, 2.0853219032287598, 2.7259600162506104, 3.544435977935791, 3.7637863159179688, 4.590723514556885, 3.1889889240264893, 4.408464431762695, 3.7832579612731934, 2.6805450916290283, 4.63645601272583, 2.903693437576294, 2.8048031330108643, 3.8929688930511475, 2.2248663902282715, 2.2367658615112305, 3.011110782623291, 2.1587440967559814, 1.871718406677246, 2.441333055496216, 3.9334511756896973, 4.760963439941406, 3.5205705165863037, 3.195653200149536, 4.116927623748779, 2.9933078289031982, 3.284879684448242, 3.0424745082855225, 1.978338599205017, 2.185760736465454, 2.8789849281311035, 2.412846565246582, 1.8859024047851562, 3.1087310314178467, 3.6956746578216553, 3.2116787433624268, 3.9088268280029297, 3.5538909435272217, 2.821601152420044, 3.6242897510528564, 3.5752780437469482, 3.324488401412964, 2.2390668392181396, 3.4549076557159424, 3.1873137950897217, 3.898743152618408, 3.1176018714904785, 3.0699596405029297, 5.1208176612854, 3.655621290206909, 595.3502807617188, 154.424560546875, 285.0682067871094, 41.439903259277344, 277.07196044921875, 305.24853515625, 372.8021545410156, 212.357666015625, 271.95849609375, 213.63047790527344, 160.158447265625, 57.4625244140625, 96.85382843017578, 91.721923828125, 165.6990966796875, 484.9059143066406, 528.9666748046875, 370.5304870605469, 268.6925048828125, 220.58233642578125, 264.9342041015625, 298.2265625, 355.056396484375, 375.0220947265625, 97.13356018066406, 63.1624755859375, 413.2438049316406, 256.4757080078125, 136.9764404296875, 110.67010498046875, 223.036865234375, 236.31092834472656, 66.03802490234375, 80.61653900146484, 161.72979736328125, 103.23573303222656, 164.25802612304688, 57.29261016845703, 230.6167755126953, 305.59967041015625, 119.33319091796875, 65.03666687011719, 235.6751708984375, 59.12227249145508, 95.36870574951172, 226.84991455078125, 362.1625061035156, 191.2010498046875, 278.7127685546875, 278.0948486328125, 836.9535522460938, 402.9291076660156, 67.77082061767578, 225.99069213867188, 420.732177734375, 384.3748779296875, 186.5593719482422, 575.689208984375, 512.016357421875, 255.5224609375, 117.97940063476562, 106.36943817138672, 396.1571044921875, 220.94541931152344, 55.2779541015625, 301.6556091308594, 251.19091796875, 168.15966796875, 447.8703308105469, 104.49798583984375, 168.99208068847656, 85.6229248046875, 325.287109375, 123.15374755859375, 380.9835510253906, 46.632381439208984, 169.8623046875, 438.5732421875, 281.4113464355469, 177.58901977539062, 77.7164306640625, 194.54237365722656, 167.4728546142578, 117.76800537109375, 453.6232604980469, 377.5769958496094, 361.8381042480469, 154.23675537109375, 187.96905517578125, 214.42105102539062, 156.99317932128906, 110.17118072509766, 645.23779296875, 105.50200653076172, 292.25311279296875, 439.2288818359375, 88.8076171875, 407.0501403808594, 259.48046875, 65.428466796875, 178.71026611328125, 372.5085144042969, 302.703857421875, 216.80291748046875, 318.29461669921875, 174.1855010986328, 100.9022216796875, 220.172607421875, 278.96929931640625, 44.948543548583984, 374.62994384765625, 207.9365997314453, 133.87774658203125, 146.6311492919922, 100.7308349609375, 325.8402099609375, 167.90081787109375, 293.82568359375, 494.120849609375, 369.7638244628906, 460.0050354003906, 97.15489959716797, 155.15673828125, 50.83319091796875, 350.4887390136719, 1227.45361328125, 350.9242858886719, 77.06089782714844, 256.59326171875, 173.8197021484375, 273.44146728515625, 170.30213928222656, 46.81472396850586, 475.6566162109375, 388.0470275878906, 85.73661041259766, 407.3110046386719, 673.3915405273438, 161.43670654296875, 177.23095703125, 1003.4514770507812, 161.6136474609375, 590.53662109375, 165.54913330078125, 212.08645629882812, 349.1427307128906, 310.9576416015625, 501.44677734375, 204.14759826660156, 175.18019104003906, 109.13201904296875, 69.41058349609375, 86.22856903076172, 310.0861511230469, 458.305419921875, 100.12413787841797, 523.445068359375, 413.04132080078125, 156.23211669921875, 243.11582946777344, 299.1739501953125, 531.1107177734375, 113.33265686035156, 387.2271728515625, 392.36468505859375, 94.14862060546875, 342.3312072753906, 143.14515686035156, 275.45611572265625, 210.75244140625, 136.35630798339844, 97.51570129394531, 138.3427734375, 67.7728271484375, 894.687255859375, 83.34027099609375, 201.1078643798828, 268.0305480957031, 634.3900146484375, 124.09498596191406, 192.62451171875, 50.69190216064453, 395.9287109375, 130.11386108398438, 209.9579620361328, 214.84754943847656, 307.02490234375, 132.00314331054688, 122.22088623046875, 144.91921997070312, 256.5921630859375, 155.115966796875, 281.6423034667969, 266.63641357421875, 89.39924621582031, 239.90179443359375, 192.3397216796875, 390.36273193359375, 251.9658203125, 170.4021453857422, 252.9646759033203, 266.8214111328125, 71.46156311035156, 382.9664306640625, 275.9539794921875, 416.76654052734375, 216.47581481933594, 268.46392822265625, 274.9154357910156, 402.7353515625, 108.2425765991211, 175.03916931152344, 154.2803497314453, 57.69678497314453, 232.4617919921875, 169.0410919189453, 105.72709655761719, 93.98431396484375, 419.4339599609375, 222.6168670654297, 62.451904296875, 153.54937744140625, 321.3682861328125, 323.626953125, 225.30235290527344, 58.2501220703125, 437.6395263671875, 203.5371856689453, 299.47174072265625, 98.55099487304688, 61.6085205078125, 232.239013671875, 595.85498046875, 103.35687255859375, 217.784912109375, 63.86884689331055, 321.0807800292969, 315.8564453125, 293.490234375, 157.18960571289062, 104.91515350341797, 434.9413146972656, 679.44482421875, 289.4529724121094, 502.5148010253906, 416.149169921875, 172.2368927001953, 677.1515502929688, 245.53057861328125, 69.60980224609375, 202.5387420654297, 276.6738586425781, 331.681396484375, 219.49191284179688, 373.0277404785156, 142.8037872314453, 74.05224609375, 113.926025390625, 353.65765380859375, 156.7179412841797, 310.54193115234375, 419.7838134765625, 58.786590576171875, 186.05010986328125, 396.6394958496094, 252.15234375, 400.56396484375, 210.4295654296875, 262.6562194824219, 154.88442993164062, 303.9246826171875, 208.26370239257812, 380.673828125, 196.6981964111328, 535.9613647460938, 155.09947204589844, 144.7417755126953, 77.76220703125, 97.4754409790039, 110.322998046875, 288.3662109375, 135.08203125, 86.901611328125, 373.14794921875, 119.594970703125, 89.69818115234375, 288.16046142578125, 350.2347717285156, 218.03050231933594, 199.05528259277344, 172.33035278320312, 369.20062255859375, 238.1063995361328, 446.4161682128906, 223.51487731933594, 358.192138671875, 543.39453125, 225.7323455810547, 200.71595764160156, 199.5272979736328, 2.014547348022461, 1.9161311388015747, 1.9996126890182495, 3.0104992389678955, 1.1429873704910278, 2.4268205165863037, 2.602593421936035, 3.2566676139831543, 2.52842116355896, 1.433705449104309, 3.2936251163482666, 1.9964746236801147, 4.475369930267334, 2.913710355758667, 2.288811683654785, 4.095893859863281, 3.354323148727417, 1.8154613971710205, 2.154470443725586, 2.8881945610046387, 3.187343120574951, 3.233799934387207, 3.0900187492370605, 2.2904675006866455, 2.0010483264923096, 3.337946653366089, 2.0910348892211914, 3.277228355407715, 1.9419126510620117, 3.7742602825164795, 3.542875289916992, 3.870051145553589, 2.034428119659424, 3.769904613494873, 1.8367934226989746, 2.9713222980499268, 2.7501165866851807, 4.0512566566467285, 1.869648814201355, 1.8157339096069336, 2.330754041671753, 3.4554827213287354, 2.072068691253662, 1.857924461364746, 1.7771836519241333, 1.9155892133712769, 3.781712293624878, 1.8389360904693604, 3.8617238998413086, 2.2225561141967773, 2.6798760890960693, 2.9192020893096924, 3.875657320022583, 3.6235668659210205, 2.344292640686035, 2.8027000427246094, 1.4784959554672241, 3.44022274017334, 3.1274328231811523, 3.46835994720459, 2.067305564880371, 3.313732624053955, 2.1420679092407227, 2.211319923400879, 2.8073067665100098, 2.329094886779785, 2.808947801589966, 2.7980589866638184, 2.7392492294311523, 1.8961982727050781, 2.9796969890594482, 3.0541601181030273, 1.8902511596679688, 1.539925456047058, 3.2308754920959473, 2.2905666828155518, 1.4586554765701294, 3.6261913776397705, 2.988077402114868, 2.2932679653167725, 1.9437381029129028, 2.382784843444824, 2.775275230407715, 1.8946833610534668, 3.455420732498169, 2.5997345447540283, 2.37158465385437, 1.8556115627288818, 2.1433846950531006, 3.585230827331543, 2.1496613025665283, 3.1892502307891846, 2.5014121532440186, 2.8287975788116455, 2.581821918487549, 3.188462495803833, 2.512759208679199, 3.0510354042053223, 2.317441701889038, 2.385319709777832, 1.9178507328033447, 2.7147045135498047, 3.608738899230957, 1.5370359420776367, 3.225053071975708, 2.537264347076416, 3.235119581222534, 2.578517198562622, 2.469686508178711, 3.480912923812866, 3.2848880290985107, 2.567051887512207, 1.7033623456954956, 3.695148468017578, 1.393575668334961, 2.8513951301574707, 1.5830074548721313, 3.183673620223999, 3.6504924297332764, 2.330195665359497, 3.058443784713745, 2.9361894130706787, 3.100957155227661, 2.211874008178711, 2.047746419906616, 2.79058837890625, 4.257430553436279, 2.6597347259521484, 3.252291202545166, 2.066807746887207, 2.122159481048584, 2.811042070388794, 3.1120975017547607, 2.115260362625122, 2.9429738521575928, 2.218334674835205, 2.8080379962921143, 2.552065372467041, 2.139148712158203, 3.1704254150390625, 2.577380657196045, 2.464755058288574, 3.193652391433716, 2.058854818344116, 3.1529741287231445, 3.424483060836792, 2.7197296619415283, 2.1134531497955322, 2.984495162963867, 3.4045522212982178, 2.4989376068115234, 2.7692179679870605, 2.5933244228363037, 2.736293315887451, 2.365993022918701, 2.7404892444610596, 2.005490303039551, 1.7948484420776367, 2.6370744705200195, 2.3629674911499023, 2.8556175231933594, 3.4530327320098877, 2.8479771614074707, 2.411086082458496, 3.9449779987335205, 3.0145931243896484, 3.0741913318634033, 1.6158673763275146, 1.5673571825027466, 1.5694347620010376, 3.616969108581543, 2.2586755752563477, 3.350642204284668, 2.233242988586426, 2.1611618995666504, 2.1210126876831055, 3.005690813064575, 1.4911527633666992, 2.9328160285949707, 2.8759586811065674, 3.9104223251342773, 2.7738499641418457, 4.0333967208862305, 1.880526065826416, 1.9972105026245117, 1.9226152896881104, 2.438382863998413, 3.5089492797851562, 2.367852210998535, 3.616683006286621, 3.244471311569214, 2.566976547241211, 3.439948081970215, 1.8562393188476562, 3.357769727706909, 2.6502468585968018, 3.1114048957824707, 2.4636950492858887, 3.399094820022583, 3.677252769470215, 2.6221940517425537, 2.6731371879577637, 2.3055691719055176, 1.874609351158142, 2.537346363067627, 2.519606351852417, 3.393850088119507, 3.4756059646606445, 2.291266441345215, 1.8160604238510132, 3.2348644733428955, 3.3670947551727295, 3.5791614055633545, 2.2187795639038086, 3.664198637008667, 2.5259556770324707, 2.903355598449707, 3.528794527053833, 3.128493547439575, 2.9273030757904053, 2.0855560302734375, 2.9944963455200195, 3.0188493728637695, 3.574313163757324, 1.947895884513855, 2.517145872116089, 3.750828742980957, 2.2583870887756348, 1.8478058576583862, 2.6898434162139893, 2.861438512802124, 2.627417802810669, 3.626776933670044, 2.838446855545044, 2.635309934616089, 2.4210729598999023, 2.4534289836883545, 3.1391422748565674, 1.904261589050293, 3.60794734954834, 1.9614369869232178, 1.8775238990783691, 2.10237979888916, 3.783381938934326, 3.6847167015075684, 3.4342041015625, 1.7597821950912476, 2.1079976558685303, 1.8364633321762085, 1.713300108909607, 3.776616096496582, 2.2686362266540527, 2.5066215991973877, 3.3205947875976562, 2.446253538131714, 1.6385998725891113, 2.414226531982422, 3.548684597015381, 2.6735892295837402, 2.9138402938842773, 3.2010862827301025, 2.9234955310821533, 1.5098562240600586, 3.467759370803833, 4.086978912353516, 2.874772310256958, 2.0646848678588867, 2.8146655559539795, 1.9801360368728638, 2.0845558643341064, 2.467475175857544, 3.392777681350708, 1.8742475509643555, 1.8908236026763916, 2.7518627643585205, 2.3125622272491455, 3.411985158920288, 3.7192089557647705, 3.358301877975464, 2.7291765213012695, 2.747361421585083, 1.5716009140014648, 1.3809844255447388, 2.465196132659912, 3.5840954780578613, 2.447864055633545, 1.9085493087768555, 1.5177758932113647, 3.375870943069458, 3.5585412979125977, 3.4367504119873047, 2.9639384746551514, 2.4475810527801514, 2.5869781970977783, 3.4982542991638184, 2.8753063678741455, 2.2318060398101807, 3.8901665210723877, 2.4530935287475586, 2.8464977741241455, 0.22669774293899536, 0.22284667193889618, 0.26884791254997253, 0.206994891166687, 0.19125787913799286, 0.26967206597328186, 0.279979407787323, 0.19172629714012146, 0.3108226954936981, 0.2306765764951706, 0.2955109179019928, 0.23910993337631226, 0.17464759945869446, 0.23485167324543, 0.1649503856897354, 0.21431231498718262, 0.23640139400959015, 0.25517740845680237, 0.23451121151447296, 0.2784971296787262, 0.2665576934814453, 0.20590251684188843, 0.2581438720226288, 0.2637792229652405, 0.23970846831798553, 0.24225227534770966, 0.32712990045547485, 0.23453998565673828, 0.2568080425262451, 0.2427876591682434, 0.19227226078510284, 0.248153954744339, 0.20661599934101105, 0.22683066129684448, 0.21150963008403778, 0.2736521065235138, 0.22678439319133759, 0.3085455000400543, 0.22024787962436676, 0.266571968793869, 0.2898666560649872, 0.3115255534648895, 0.23550128936767578, 0.25993794202804565, 0.2056722640991211, 0.2837705612182617, 0.24483592808246613, 0.26204222440719604, 0.24004262685775757, 0.3127068877220154, 0.2708686888217926, 0.22167430818080902, 0.24069248139858246, 0.2687094807624817, 0.3193904459476471, 0.20725925266742706, 0.22752295434474945, 0.2967182993888855, 0.2286607325077057, 0.19217677414417267, 0.2432473748922348, 0.29633331298828125, 0.29900312423706055, 0.25634074211120605, 0.3284205496311188, 0.21127933263778687, 0.2405027598142624, 0.20652270317077637, 0.20309996604919434, 0.19853878021240234, 0.3150969445705414, 0.2643148601055145, 0.2221265733242035, 0.3062134385108948, 0.2756761312484741, 0.21929195523262024, 0.22592826187610626, 0.26271721720695496, 0.2562243938446045, 0.2521732449531555, 0.2562156915664673, 0.21038688719272614, 0.2554051876068115, 0.2632264792919159, 0.2593555748462677, 0.22103357315063477, 0.30865707993507385, 0.2678924798965454, 0.1964101344347, 0.2922126054763794, 0.22578543424606323, 0.23214231431484222, 0.24913039803504944, 0.2067795842885971, 0.20631445944309235, 0.17308521270751953, 0.23609359562397003, 0.29425451159477234, 0.24913020431995392, 0.24001960456371307, 0.262153685092926, 0.2530774772167206, 0.2749730050563812, 0.25025951862335205, 0.26774898171424866, 0.28766104578971863, 0.25917527079582214, 0.2523854076862335, 0.25106215476989746, 0.2559680640697479, 0.2612661123275757, 0.23602771759033203, 0.2337503731250763, 0.3293321132659912, 0.21860730648040771, 0.2614451050758362, 0.24198710918426514, 0.17676886916160583, 0.28238317370414734, 0.2516610026359558, 0.2034207433462143, 0.2143903523683548, 0.21794600784778595, 0.25458675622940063, 0.3055504560470581, 0.27653443813323975, 0.23509939014911652, 0.26419514417648315, 0.2971131503582001, 0.24551630020141602, 0.2742309272289276, 0.19657619297504425, 0.2356841266155243, 0.21660158038139343, 0.18814368546009064, 0.2550317943096161, 0.28607484698295593, 0.3109942674636841, 0.20306521654129028, 0.22264625132083893, 0.2498822957277298, 0.2272357940673828, 0.2688480019569397, 0.22156596183776855, 0.28719040751457214, 0.2454913854598999, 0.21983303129673004, 0.257312536239624, 0.21347689628601074, 0.31228965520858765, 0.25270572304725647, 0.24046897888183594, 0.22837822139263153, 0.22574679553508759, 0.25347504019737244, 0.2639870047569275, 0.230050727725029, 0.2104150950908661, 0.17887091636657715, 0.2053987830877304, 0.15789420902729034, 0.31282421946525574, 0.28501367568969727, 0.22415655851364136, 0.2147291898727417, 0.260013222694397, 0.27875474095344543, 0.24717020988464355, 0.308570921421051, 0.24864383041858673, 0.24414145946502686, 0.3060847818851471, 0.23619285225868225, 0.2703537940979004, 0.24925559759140015, 0.22238022089004517, 0.2405349612236023, 0.27725958824157715, 0.2861792743206024, 0.2294905036687851, 0.17839376628398895, 0.2142893224954605, 0.25574401021003723, 0.30367937684059143, 0.22889304161071777, 0.2415073662996292, 0.2831918001174927, 0.2567572593688965, 0.23020145297050476, 0.22874172031879425, 0.33696380257606506, 0.26983174681663513, 0.30385860800743103, 0.23865948617458344, 0.24172423779964447, 0.2521219849586487, 0.25727054476737976, 0.30584287643432617, 0.2828776240348816, 0.26924726366996765, 0.12475065141916275, 0.2588155269622803, 0.22754168510437012, 0.2428976446390152, 0.2994097173213959, 0.1798461526632309, 0.2219354510307312, 0.23824071884155273, 0.24819499254226685, 0.25883352756500244, 0.27284854650497437, 0.27511751651763916, 0.29320991039276123, 0.21984131634235382, 0.20847304165363312, 0.23786696791648865, 0.2919510304927826, 0.2284005731344223, 0.2746109366416931, 0.2734553813934326, 0.2625572383403778, 0.2156774401664734, 0.27689453959465027, 0.31283122301101685, 0.2534319758415222, 0.2544668912887573, 0.27020156383514404, 0.2181125432252884, 0.286685585975647, 0.21914142370224, 0.2867007255554199, 0.208021879196167, 0.21989615261554718, 0.2060500979423523, 0.24143917858600616, 0.2810969948768616, 0.268514484167099, 0.32345283031463623, 0.2888414263725281, 0.2696853578090668, 0.2535749077796936, 0.27536025643348694, 0.24335983395576477, 0.27603328227996826, 0.22498317062854767, 0.21905814111232758, 0.253263920545578, 0.22889403998851776, 0.3453086018562317, 0.20263957977294922, 0.18541717529296875, 0.3384418487548828, 0.1945178359746933, 0.3088711202144623, 0.2161215990781784, 0.2590404152870178, 0.2428777664899826, 0.3792687654495239, 0.2829119563102722, 0.21188177168369293, 0.22339916229248047, 0.29294607043266296, 0.2633495330810547, 0.24686656892299652, 0.2989087700843811, 0.25248968601226807, 0.35239988565444946, 0.20976504683494568, 0.2043040245771408, 0.23177073895931244, 0.22413364052772522, 0.2700309455394745, 0.22246675193309784, 0.2331387996673584, 0.31156864762306213, 0.29040321707725525, 0.24999022483825684, 0.2581472396850586, 0.23280103504657745, 0.2105468511581421, 0.23620149493217468, 0.2377261370420456, 0.2035306841135025, 0.23767638206481934, 0.220430389046669, 0.31433334946632385, 0.21894629299640656, 0.2730801999568939, 0.24848678708076477, 0.1859719604253769, 0.2760419547557831, 0.24740977585315704, 0.32428282499313354, 0.25426122546195984, 0.292635977268219, 0.18172553181648254, 0.27034568786621094, 0.25741979479789734, 0.2698317766189575, 0.3246456980705261, 3.4300918579101562, 3.6155028343200684, 2.9408950805664062, 4.078972339630127, 3.8056187629699707, 2.729201555252075, 2.3146679401397705, 3.3356738090515137, 2.949498414993286, 2.2437691688537598, 4.984374046325684, 2.9911632537841797, 4.288821697235107, 3.9853856563568115, 3.7531490325927734, 3.051062822341919, 4.5582275390625, 1.5838009119033813, 4.362641334533691, 4.448997497558594, 3.1905293464660645, 2.891761064529419, 3.0161845684051514, 2.8682777881622314, 2.320281744003296, 2.891436815261841, 3.4711430072784424, 3.579944372177124, 3.0818862915039062, 1.8186450004577637, 2.1798524856567383, 2.583331346511841, 3.322535514831543, 3.2949821949005127, 3.947681188583374, 2.175615072250366, 2.008875846862793, 3.4078450202941895, 3.3428502082824707, 3.1730282306671143, 3.453871965408325, 2.9169399738311768, 4.270722389221191, 3.018315553665161, 3.980008363723755, 5.172703742980957, 4.090882301330566, 2.867474317550659, 3.9043197631835938, 1.9273537397384644, 3.037616729736328, 4.062017440795898, 2.0558247566223145, 2.3774402141571045, 3.9111411571502686, 4.110895156860352, 2.6576004028320312, 2.990673780441284, 2.8032209873199463, 3.7807018756866455, 3.894714832305908, 2.679539203643799, 3.5198898315429688, 3.574841260910034, 1.9294488430023193, 3.301008939743042, 3.090991258621216, 3.0194244384765625, 2.340362310409546, 2.728787899017334, 3.461806058883667, 3.6042802333831787, 3.264446258544922, 4.396729469299316, 4.558486461639404, 3.8264739513397217, 4.398523330688477, 3.4848124980926514, 2.9200146198272705, 2.579327344894409, 2.6686763763427734, 2.3319804668426514, 3.3421504497528076, 2.3506264686584473, 3.3281431198120117, 3.754288911819458, 3.5326755046844482, 2.907620668411255, 3.057767868041992, 3.2105560302734375, 1.7193987369537354, 3.9771294593811035, 3.4188525676727295, 2.1823136806488037, 2.8349430561065674, 2.2854132652282715, 2.6500420570373535, 3.1584198474884033, 4.9291510581970215, 3.8106987476348877, 2.2636184692382812, 2.4649746417999268, 2.6829795837402344, 3.6520144939422607, 3.6159756183624268, 4.153757095336914, 3.9926087856292725, 2.7764644622802734, 2.5720133781433105, 3.8210995197296143, 3.2562267780303955, 4.046450614929199, 2.8494808673858643, 3.7466981410980225, 3.195923328399658, 2.6387975215911865, 4.518362522125244, 3.3382632732391357, 4.571167945861816, 3.976703405380249, 2.8213446140289307, 2.2145063877105713, 3.2774734497070312, 2.5997066497802734, 2.9831740856170654, 2.814638614654541, 3.1250195503234863, 3.207038164138794, 2.775261402130127, 4.781862258911133, 3.49096941947937, 2.318938970565796, 2.257150888442993, 4.174775123596191, 2.352872610092163, 2.977966785430908, 2.6470983028411865, 3.304572582244873, 3.517319917678833, 3.4115588665008545, 3.581372022628784, 2.941516637802124, 3.965610980987549, 2.442673683166504, 2.538273811340332, 2.867216110229492, 2.813532590866089, 2.9564731121063232, 2.840648651123047, 3.0184788703918457, 3.35650897026062, 3.3735454082489014, 4.085785865783691, 2.3363897800445557, 2.737248420715332, 3.5640766620635986, 2.7807648181915283, 3.4164257049560547, 2.355499267578125, 4.167046070098877, 3.260939359664917, 2.77520751953125, 3.2323226928710938, 2.9945528507232666, 2.684678792953491, 2.5889923572540283, 4.629179954528809, 3.134674549102783, 4.068880558013916, 2.2690954208374023, 2.993892192840576, 2.3763527870178223, 1.9425714015960693, 5.242737770080566, 2.3584234714508057, 5.269433498382568, 2.5185067653656006, 3.809696674346924, 3.0435245037078857, 2.0209264755249023, 3.756150484085083, 4.300321578979492, 2.360900402069092, 4.396821975708008, 3.455115556716919, 4.311279773712158, 2.889211654663086, 2.302968978881836, 2.9336748123168945, 4.190433025360107, 2.8495876789093018, 4.625144004821777, 3.607358932495117, 4.0750837326049805, 3.9934017658233643, 2.6310276985168457, 3.773115873336792, 3.3363113403320312, 3.35955548286438, 3.768829822540283, 2.0366504192352295, 4.500898361206055, 2.7520077228546143, 3.319979667663574, 2.936267614364624, 3.456434965133667, 3.6533501148223877, 4.114730358123779, 3.286785840988159, 2.47029447555542, 3.7429027557373047, 2.0237832069396973, 3.254026412963867, 3.6173722743988037, 3.1815319061279297, 3.5284721851348877, 3.1403934955596924, 3.118673086166382, 4.546302318572998, 2.865108013153076, 4.226638317108154, 3.6978039741516113, 4.520643711090088, 3.5198380947113037, 3.986448287963867, 2.2215185165405273, 2.395707607269287, 3.517181873321533, 2.8724822998046875, 3.411236524581909, 2.514366388320923, 2.619136095046997, 4.03670072555542, 3.826005220413208, 2.367978811264038, 3.4727604389190674, 4.757812976837158, 4.957491397857666, 3.359454870223999, 3.205203056335449, 3.9405205249786377, 2.9775173664093018, 4.133430480957031, 3.3453404903411865, 4.395569801330566, 1.842745304107666, 2.8882064819335938, 2.496306896209717, 3.472324848175049, 2.1290953159332275, 2.3442397117614746, 3.8581619262695312, 4.477416515350342, 2.212883472442627, 2.8752694129943848, 2.7771904468536377, 2.565080404281616, 3.8144054412841797, 3.3236541748046875, 2.8534469604492188, 3.394970655441284, 3.3657596111297607, 3.027259111404419, 2.6148617267608643, 4.3909912109375, 3.4110164642333984, 2.2675440311431885, 2.9831249713897705, 4.134669303894043, 2.8563733100891113, 4.325209140777588, 3.614140033721924, 2.4158730506896973, 2.483332633972168, 3.2769405841827393, 4.358452320098877, 3.723170757293701, 2.2238996028900146, 3.427643299102783, 2.2559971809387207, 3.3235061168670654, 4.3104071617126465, 2.922583818435669, 1.8983397483825684, 2.801682710647583, 3.2736153602600098, 3.5797882080078125, 4.0973944664001465, 2.1677210330963135, 4.877774238586426, 2.2878451347351074, 4.266363143920898, 2.355600595474243, 2.4484879970550537, 4.643391132354736, 3.6581053733825684, 2.4480552673339844, 3.960136890411377, 2.2722129821777344, 4.093508243560791, 187.0697479248047, 386.6715393066406, 334.3695983886719, 378.9595947265625, 298.3821716308594, 169.5614013671875, 86.62334442138672, 507.5553283691406, 127.9310531616211, 273.2916259765625, 197.8269500732422, 56.68499755859375, 438.6086120605469, 457.10870361328125, 261.4263916015625, 175.22190856933594, 107.85411834716797, 174.93655395507812, 235.37464904785156, 152.3234100341797, 74.6529541015625, 597.89453125, 59.178836822509766, 39.18194580078125, 201.6554718017578, 289.5617370605469, 281.42706298828125, 92.85991668701172, 102.1854248046875, 169.48843383789062, 250.4399871826172, 324.33892822265625, 301.38623046875, 131.08995056152344, 209.39874267578125, 323.9287109375, 96.73681640625, 312.4033203125, 429.2503662109375, 462.0462646484375, 119.33387756347656, 116.5751953125, 145.71331787109375, 303.0594482421875, 56.93323516845703, 200.7077178955078, 288.07562255859375, 170.19882202148438, 58.05654525756836, 249.9662628173828, 110.52851104736328, 234.71902465820312, 299.9153137207031, 127.69305419921875, 363.1550598144531, 161.1224365234375, 163.2260284423828, 81.52887725830078, 254.9451141357422, 162.9950408935547, 129.8924560546875, 273.632568359375, 233.09886169433594, 164.73355102539062, 163.35968017578125, 239.72178649902344, 584.2257080078125, 62.49456787109375, 290.91961669921875, 114.86395263671875, 151.4118194580078, 151.14321899414062, 538.3040771484375, 153.42881774902344, 204.13992309570312, 123.7628173828125, 106.82171630859375, 377.6935119628906, 141.7094268798828, 187.8058624267578, 399.24249267578125, 120.13703155517578, 242.0262908935547, 144.65869140625, 365.6279296875, 67.76265716552734, 296.70660400390625, 310.9728698730469, 137.60757446289062, 151.48207092285156, 232.37913513183594, 124.3701171875, 129.862060546875, 76.17023468017578, 466.853515625, 391.97210693359375, 204.49473571777344, 315.74163818359375, 245.0751495361328, 110.69425201416016, 388.2877197265625, 223.40380859375, 328.7510986328125, 429.6144714355469, 223.80322265625, 125.07095336914062, 267.8428955078125, 332.3648376464844, 457.4823303222656, 170.03330993652344, 105.1845703125, 121.08312225341797, 300.31005859375, 168.10604858398438, 73.1082763671875, 201.53677368164062, 555.926513671875, 144.69873046875, 454.58453369140625, 54.46821975708008, 724.3831176757812, 83.7755355834961, 287.494873046875, 368.4423828125, 344.2398376464844, 676.1858520507812, 340.2706604003906, 69.3790283203125, 108.01356506347656, 589.2832641601562, 189.24234008789062, 78.35234832763672, 197.06982421875, 476.0411682128906, 228.05401611328125, 197.8448028564453, 250.7353057861328, 197.1709747314453, 332.9925842285156, 223.6575927734375, 382.0555725097656, 211.93124389648438, 88.9426040649414, 235.31558227539062, 387.68310546875, 150.90646362304688, 253.5374755859375, 192.59033203125, 123.80821990966797, 191.69639587402344, 469.0924072265625, 525.0762939453125, 175.0674591064453, 192.98744201660156, 150.55157470703125, 363.2527770996094, 407.7525939941406, 410.1512451171875, 133.35247802734375, 204.2100372314453, 225.66937255859375, 267.3492431640625, 511.33740234375, 137.92303466796875, 340.0980529785156, 393.8742370605469, 352.6446838378906, 329.43328857421875, 350.0419006347656, 86.59564208984375, 326.491943359375, 98.5425796508789, 123.86737060546875, 283.08416748046875, 245.39010620117188, 206.40257263183594, 238.8245849609375, 421.875, 736.2424926757812, 486.055419921875, 141.95767211914062, 137.70242309570312, 287.5004577636719, 200.3367919921875, 391.6235046386719, 140.02687072753906, 94.58794403076172, 338.6222839355469, 389.896240234375, 105.45758819580078, 494.1817932128906, 597.494140625, 294.4950256347656, 111.5013427734375, 185.4739990234375, 260.7802429199219, 114.46369171142578, 132.357177734375, 208.53857421875, 560.952880859375, 152.37835693359375, 247.28363037109375, 241.93487548828125, 274.3871154785156, 239.3065185546875, 87.7650146484375, 399.7345275878906, 274.4718017578125, 578.8638916015625, 371.6461486816406, 280.3390808105469, 538.443603515625, 348.1642150878906, 115.14468383789062, 218.4715576171875, 157.1357421875, 240.23272705078125, 232.1087646484375, 332.1710205078125, 236.9209747314453, 265.4236145019531, 269.1524963378906, 205.30479431152344, 275.4940185546875, 222.043701171875, 472.07373046875, 198.8957061767578, 96.06459045410156, 114.3992919921875, 453.00146484375, 97.4452896118164, 316.4985046386719, 249.70323181152344, 136.90191650390625, 80.8935546875, 254.37307739257812, 224.1068115234375, 285.5859375, 119.03857421875, 234.85205078125, 129.70916748046875, 195.5924835205078, 292.1135559082031, 1025.394287109375, 272.2293701171875, 146.68408203125, 443.1119689941406, 203.9583740234375, 140.0778350830078, 320.61627197265625, 235.209228515625, 255.22265625, 148.34912109375, 142.5279998779297, 134.49261474609375, 626.7025756835938, 148.5802459716797, 169.24066162109375, 456.2794494628906, 105.86504364013672, 289.19000244140625, 94.36779022216797, 111.9207763671875, 72.4534683227539, 67.81781005859375, 206.065185546875, 113.79033660888672, 44.42962646484375, 140.66644287109375, 148.7223663330078, 156.96469116210938, 62.763694763183594, 93.6424331665039, 187.01036071777344, 103.87646484375, 145.61138916015625, 367.6554870605469, 352.7465515136719, 593.68896484375, 205.91546630859375, 254.8154296875, 120.47344207763672, 192.3768310546875, 312.11578369140625, 266.03973388671875, 108.35565948486328, 390.51373291015625, 544.0633544921875, 118.50952911376953, 89.10575103759766, 186.33555603027344, 919.1632690429688, 245.405029296875, 302.58697509765625, 192.2703094482422, 500.5244140625, 96.923583984375, 204.4422149658203, 408.47467041015625, 264.192626953125, 2.306180477142334, 3.6855857372283936, 2.4407033920288086, 3.456454277038574, 2.6221349239349365, 3.0511529445648193, 2.250811815261841, 4.014265537261963, 3.8281917572021484, 1.7779475450515747, 3.076709032058716, 1.7363348007202148, 2.385240316390991, 2.244694709777832, 2.5342507362365723, 2.716642379760742, 2.260181427001953, 4.106526851654053, 3.038541078567505, 1.6828163862228394, 2.65533447265625, 3.3946070671081543, 3.6403286457061768, 2.0873610973358154, 2.361903667449951, 2.181553840637207, 3.4008073806762695, 1.8818484544754028, 2.974778413772583, 1.9504042863845825, 2.5051662921905518, 3.0714635848999023, 2.3865535259246826, 3.523207426071167, 2.083646059036255, 2.767301082611084, 2.214247703552246, 3.3715391159057617, 2.4186136722564697, 1.688120722770691, 2.872088670730591, 1.5945383310317993, 2.526109218597412, 3.8358166217803955, 2.4227418899536133, 2.4042654037475586, 2.204411506652832, 3.0696816444396973, 1.8798669576644897, 2.734750986099243, 2.515913963317871, 3.588507652282715, 2.806473970413208, 2.018167734146118, 3.8162789344787598, 2.5581865310668945, 2.6601476669311523, 2.111598253250122, 1.944350242614746, 4.024683952331543, 3.5281786918640137, 3.5562849044799805, 3.0901196002960205, 2.7348296642303467, 2.126633882522583, 2.245692253112793, 1.519471526145935, 2.6445226669311523, 1.5154829025268555, 2.92675518989563, 3.297968864440918, 2.2310421466827393, 3.773413896560669, 2.3684606552124023, 2.525116443634033, 3.4555349349975586, 2.5214362144470215, 2.6720592975616455, 2.7296082973480225, 2.787543296813965, 2.40849232673645, 2.689478635787964, 3.067906379699707, 3.137775182723999, 2.5481228828430176, 2.354853868484497, 2.6864635944366455, 2.4638173580169678, 1.941421627998352, 3.4405431747436523, 2.1054277420043945, 3.3017208576202393, 2.5258309841156006, 2.8880226612091064, 2.937769651412964, 3.298468828201294, 3.197009325027466, 2.644610643386841, 3.218693256378174, 2.610224485397339, 1.1630791425704956, 3.1336584091186523, 1.6601362228393555, 1.676538348197937, 2.1822519302368164, 2.38954496383667, 2.0686450004577637, 2.428579092025757, 1.7760974168777466, 1.9723113775253296, 3.0388057231903076, 1.7401248216629028, 3.33181095123291, 3.3465452194213867, 4.280725479125977, 3.9052085876464844, 3.3853251934051514, 2.512131690979004, 3.369053840637207, 3.330036163330078, 2.1444389820098877, 2.065032958984375, 2.865679979324341, 2.5085608959198, 3.4553442001342773, 3.4967527389526367, 2.769242525100708, 1.9000017642974854, 1.9908196926116943, 4.221133232116699, 3.80515193939209, 2.652751922607422, 3.23368763923645, 1.9452085494995117, 1.9549096822738647, 2.4513750076293945, 2.9728012084960938, 1.9318664073944092, 3.507330894470215, 3.20825457572937, 3.502852201461792, 2.4335131645202637, 2.2054688930511475, 2.9519872665405273, 2.462871551513672, 3.8949291706085205, 2.7493982315063477, 1.8604063987731934, 3.3702588081359863, 2.536013603210449, 1.838664174079895, 1.8733348846435547, 2.869643449783325, 3.0288238525390625, 3.050701856613159, 2.791475534439087, 2.724047899246216, 1.7161022424697876, 2.8620216846466064, 3.301290273666382, 2.5316460132598877, 2.6969010829925537, 1.7906599044799805, 2.970477342605591, 2.8754544258117676, 2.7895848751068115, 3.2696099281311035, 2.0216970443725586, 2.363276243209839, 3.5529255867004395, 2.8723678588867188, 2.638871908187866, 3.3031420707702637, 2.7652904987335205, 2.25740909576416, 1.9413671493530273, 3.9406685829162598, 1.5827703475952148, 2.4143707752227783, 2.0563559532165527, 3.762883186340332, 2.46114182472229, 2.0760343074798584, 1.4103612899780273, 2.9384822845458984, 4.010453224182129, 3.274073362350464, 2.8047420978546143, 2.196385383605957, 3.912814140319824, 2.975186586380005, 3.3940839767456055, 3.980811357498169, 3.236961841583252, 3.0742547512054443, 1.817685842514038, 2.243157386779785, 3.00924015045166, 2.603308916091919, 2.270707607269287, 3.702216386795044, 3.877274990081787, 3.1898128986358643, 1.6189340353012085, 1.7856453657150269, 3.2811460494995117, 2.981480121612549, 2.4615190029144287, 1.7748708724975586, 3.1289873123168945, 2.477414131164551, 3.635775566101074, 3.759538173675537, 3.018866777420044, 2.391568660736084, 2.168992280960083, 3.0662927627563477, 3.6808042526245117, 2.273056983947754, 1.9728879928588867, 1.8888007402420044, 1.620821475982666, 3.5142135620117188, 2.4151852130889893, 2.1936655044555664, 2.177361488342285, 3.146270751953125, 2.963033437728882, 2.279205083847046, 3.1363134384155273, 3.7218873500823975, 2.6818268299102783, 4.1468505859375, 1.9257210493087769, 2.6192662715911865, 2.916318893432617, 3.814091682434082, 1.796466588973999, 2.4197473526000977, 2.8949480056762695, 2.9121475219726562, 3.4393069744110107, 2.1216259002685547, 2.965529680252075, 2.224188804626465, 2.775254487991333, 2.6973931789398193, 3.9907615184783936, 2.773266553878784, 3.839350461959839, 2.8995463848114014, 2.1814451217651367, 2.465226173400879, 2.2615835666656494, 2.478764295578003, 2.839585542678833, 2.5741636753082275, 3.5528934001922607, 2.2822933197021484, 2.086202383041382, 2.0741920471191406, 2.90160870552063, 2.370147228240967, 2.4358601570129395, 3.489274263381958, 1.6530332565307617, 2.29834246635437, 2.3634440898895264, 1.9446203708648682, 3.2774477005004883, 1.9521185159683228, 3.4116172790527344, 3.3921360969543457, 3.2266666889190674, 3.878783702850342, 2.2468254566192627, 3.197361469268799, 2.7789735794067383, 3.8042690753936768, 2.7463104724884033, 3.5897293090820312, 1.9477733373641968, 2.796156644821167, 2.398587942123413, 2.1297881603240967, 1.2120699882507324, 1.4605157375335693, 2.512920379638672, 3.0297720432281494, 1.8840190172195435, 2.897618532180786, 3.3779852390289307, 3.0888824462890625, 2.885420560836792, 2.0156469345092773, 2.125779151916504, 1.9869022369384766, 2.66935658454895, 2.3445825576782227, 2.6717183589935303, 0.1661444455385208, 0.2383485734462738, 0.24978899955749512, 0.2853778302669525, 0.24282582104206085, 0.2363096922636032, 0.22424788773059845, 0.2621012330055237, 0.2391463965177536, 0.2539070248603821, 0.2391727715730667, 0.2274320125579834, 0.2610451877117157, 0.23996122181415558, 0.25684863328933716, 0.22879722714424133, 0.24325931072235107, 0.2714367210865021, 0.1826554834842682, 0.20190109312534332, 0.2830830216407776, 0.2734450399875641, 0.2934997081756592, 0.2524148225784302, 0.2400507926940918, 0.2526906728744507, 0.2135569006204605, 0.2753189504146576, 0.19335079193115234, 0.22948329150676727, 0.23768869042396545, 0.30278339982032776, 0.2610226273536682, 0.3270905613899231, 0.36199644207954407, 0.263638973236084, 0.16024482250213623, 0.26458853483200073, 0.31162384152412415, 0.20714718103408813, 0.2670198678970337, 0.22192835807800293, 0.21143431961536407, 0.27221810817718506, 0.22938627004623413, 0.2062113732099533, 0.2536208927631378, 0.2297775149345398, 0.29469728469848633, 0.2391994744539261, 0.254686564207077, 0.2525523602962494, 0.2926044762134552, 0.25715315341949463, 0.2675914466381073, 0.2508069574832916, 0.20375899970531464, 0.26119929552078247, 0.2141949087381363, 0.2733061611652374, 0.2782227396965027, 0.24043376743793488, 0.21618369221687317, 0.21832622587680817, 0.30236101150512695, 0.22721484303474426, 0.24991048872470856, 0.26215341687202454, 0.32828211784362793, 0.2326722890138626, 0.22065682709217072, 0.25603893399238586, 0.1924201101064682, 0.2365189492702484, 0.2195197194814682, 0.2671588957309723, 0.3239160180091858, 0.23962177336215973, 0.21949274837970734, 0.26506614685058594, 0.21930404007434845, 0.23344600200653076, 0.1941065490245819, 0.2425638884305954, 0.24743178486824036, 0.2273171991109848, 0.23450854420661926, 0.22533118724822998, 0.2902683615684509, 0.2702411711215973, 0.30210718512535095, 0.2586471736431122, 0.2783963084220886, 0.32947784662246704, 0.24312667548656464, 0.27137649059295654, 0.2961256802082062, 0.23270383477210999, 0.26455798745155334, 0.26419708132743835, 0.30295658111572266, 0.21827925741672516, 0.1815347820520401, 0.27083513140678406, 0.1939234435558319, 0.22912496328353882, 0.3005322813987732, 0.23621253669261932, 0.2411079853773117, 0.24637283384799957, 0.2976053059101105, 0.25339239835739136, 0.26322275400161743, 0.2723461389541626, 0.25708281993865967, 0.3499315679073334, 0.2690877914428711, 0.27207404375076294, 0.2419465035200119, 0.2449377030134201, 0.22608767449855804, 0.19438186287879944, 0.3030807375907898, 0.26189547777175903, 0.2616371810436249, 0.27297547459602356, 0.24885506927967072, 0.23072025179862976, 0.17291739583015442, 0.22924304008483887, 0.2832946479320526, 0.24591697752475739, 0.30190515518188477, 0.23116058111190796, 0.265790194272995, 0.21225404739379883, 0.27709123492240906, 0.28985628485679626, 0.2510192394256592, 0.28611037135124207, 0.28508660197257996, 0.25070297718048096, 0.24281920492649078, 0.2109982818365097, 0.30460160970687866, 0.28903529047966003, 0.2939513027667999, 0.232050821185112, 0.29416486620903015, 0.28175032138824463, 0.26079151034355164, 0.30884361267089844, 0.2208717316389084, 0.3381684720516205, 0.25842025876045227, 0.25362756848335266, 0.3274903893470764, 0.21317878365516663, 0.1971479207277298, 0.3109505772590637, 0.23539920151233673, 0.22425122559070587, 0.21137240529060364, 0.26038554310798645, 0.3138960301876068, 0.3094969689846039, 0.22011202573776245, 0.20527233183383942, 0.22152996063232422, 0.29123470187187195, 0.28184008598327637, 0.3104693293571472, 0.25613489747047424, 0.21675848960876465, 0.28100496530532837, 0.2438727766275406, 0.18072935938835144, 0.2606891393661499, 0.28311002254486084, 0.1910063475370407, 0.2284463793039322, 0.26223984360694885, 0.28390419483184814, 0.28934597969055176, 0.24345819652080536, 0.30685853958129883, 0.2879560887813568, 0.2863806188106537, 0.26861637830734253, 0.2628340721130371, 0.19478800892829895, 0.22070716321468353, 0.24650214612483978, 0.2184799462556839, 0.22850337624549866, 0.26019585132598877, 0.229206845164299, 0.3038095235824585, 0.22356931865215302, 0.20084251463413239, 0.23204398155212402, 0.2872801125049591, 0.1737418919801712, 0.2777925133705139, 0.21812625229358673, 0.21471285820007324, 0.16947242617607117, 0.23443011939525604, 0.2512982487678528, 0.25059595704078674, 0.22943679988384247, 0.31498461961746216, 0.26137614250183105, 0.2761274576187134, 0.3014748990535736, 0.2651236951351166, 0.20145876705646515, 0.2712385058403015, 0.32781481742858887, 0.299450159072876, 0.2495069056749344, 0.2256826013326645, 0.20875003933906555, 0.19532664120197296, 0.30077314376831055, 0.23637543618679047, 0.2572508156299591, 0.24459758400917053, 0.22324040532112122, 0.2651761770248413, 0.2900026738643646, 0.27227160334587097, 0.19949255883693695, 0.3001084327697754, 0.2215333729982376, 0.2760944664478302, 0.2782967984676361, 0.28854313492774963, 0.1922254115343094, 0.19433759152889252, 0.2828317880630493, 0.26710402965545654, 0.3071076571941376, 0.22071245312690735, 0.22266143560409546, 0.2472672164440155, 0.22040607035160065, 0.259708046913147, 0.24894961714744568, 0.22270004451274872, 0.2352171689271927, 0.2287895530462265, 0.21726207435131073, 0.3300666809082031, 0.28914764523506165, 0.20549657940864563, 0.2672460079193115, 0.22129814326763153, 0.2280082106590271, 0.29828453063964844, 0.25159385800361633, 0.2582522928714752, 0.2772735059261322, 0.2611929774284363, 0.24369418621063232, 0.27568256855010986, 0.2601938843727112, 0.21652017533779144, 0.26873141527175903, 0.2765040099620819, 0.21677610278129578, 0.2004452496767044, 0.2416657656431198, 0.22219283878803253, 0.2860492765903473, 0.257112979888916, 0.18955260515213013, 0.25555193424224854, 0.21831655502319336, 0.27304670214653015, 0.2882094383239746, 0.2216954380273819, 0.21436725556850433, 0.19561423361301422, 0.2702704668045044, 0.2535572052001953, 0.2705397605895996, 0.24655699729919434, 0.25009000301361084, 0.165793314576149, 0.24316298961639404, 0.28724002838134766, 0.3062804043292999, 0.2979888319969177, 0.18128547072410583, 0.24514208734035492, 0.34481048583984375, 0.25610652565956116, 0.2606300413608551, 0.2643270790576935, 3.411346435546875, 4.103536605834961, 2.535001754760742, 4.226068019866943, 2.913642168045044, 3.9063720703125, 2.2164885997772217, 2.762650728225708, 3.991494655609131, 3.109309673309326, 2.149838924407959, 2.86474609375, 2.5998480319976807, 3.755558967590332, 2.4158809185028076, 2.520219564437866, 5.147150993347168, 3.1173205375671387, 2.6877377033233643, 3.7517030239105225, 2.543442964553833, 3.4418797492980957, 2.492232084274292, 2.5344743728637695, 3.255530595779419, 3.2250776290893555, 2.2591285705566406, 4.6229352951049805, 3.032291889190674, 2.639331102371216, 3.215963125228882, 2.5539562702178955, 2.783320903778076, 3.1419804096221924, 2.381241798400879, 2.867863655090332, 2.2610859870910645, 4.756546974182129, 2.750908136367798, 2.4850873947143555, 2.3288426399230957, 2.742234468460083, 4.8427324295043945, 2.1726715564727783, 2.479081153869629, 5.064876556396484, 3.811282157897949, 2.667140483856201, 2.332108974456787, 2.4053030014038086, 2.509749412536621, 3.7743072509765625, 3.751105546951294, 3.766357421875, 4.820344924926758, 3.016622543334961, 3.1758739948272705, 2.9566280841827393, 4.687366008758545, 1.7825491428375244, 2.5671377182006836, 2.879956007003784, 3.4976696968078613, 2.956118106842041, 2.7683157920837402, 3.3430981636047363, 2.571960926055908, 3.6360855102539062, 2.996537923812866, 2.5851776599884033, 4.262816905975342, 3.107224702835083, 5.669095516204834, 2.350106954574585, 3.0197830200195312, 2.8092944622039795, 3.0508434772491455, 3.51164174079895, 2.076545000076294, 3.8228676319122314, 3.8592350482940674, 3.7472429275512695, 3.2139720916748047, 3.8251800537109375, 2.7317445278167725, 3.4106667041778564, 4.030849933624268, 2.507554292678833, 3.021404981613159, 3.4890544414520264, 3.3054614067077637, 3.9756786823272705, 2.7795441150665283, 2.7504947185516357, 3.711848735809326, 3.4516143798828125, 3.7156124114990234, 2.0187904834747314, 3.7131264209747314, 3.379939556121826, 4.184742450714111, 2.7982513904571533, 4.63300085067749, 3.183337450027466, 4.380022048950195, 2.4957823753356934, 3.5678863525390625, 3.1902787685394287, 5.4526286125183105, 2.7647786140441895, 2.2459890842437744, 2.8468523025512695, 3.3518757820129395, 3.5792717933654785, 2.8231358528137207, 3.7509143352508545, 4.817863941192627, 2.956238269805908, 2.192084312438965, 2.7228729724884033, 2.5938494205474854, 3.4487340450286865, 3.652679443359375, 4.1120405197143555, 2.179546594619751, 3.1051406860351562, 3.5896096229553223, 3.6911091804504395, 3.0334384441375732, 3.4269464015960693, 3.7456300258636475, 3.6062889099121094, 3.1017074584960938, 3.637371778488159, 3.8740196228027344, 2.6660149097442627, 2.410226583480835, 3.674480438232422, 4.383687496185303, 2.8683104515075684, 2.462176561355591, 3.971872091293335, 2.781589984893799, 3.505390167236328, 4.370008945465088, 4.301201343536377, 2.7265002727508545, 3.261214017868042, 5.110504150390625, 3.3718838691711426, 3.3300621509552, 3.5968093872070312, 2.7980973720550537, 3.9582793712615967, 2.770001173019409, 2.5928454399108887, 3.305908203125, 3.15958571434021, 3.2955358028411865, 3.7948760986328125, 3.5789289474487305, 2.3563644886016846, 2.9740960597991943, 3.159902334213257, 2.777496337890625, 3.4757466316223145, 3.2968876361846924, 2.8955094814300537, 2.4110751152038574, 3.1254241466522217, 2.9717626571655273, 2.531268358230591, 2.3586275577545166, 3.746887683868408, 2.8517978191375732, 2.490452766418457, 2.593935489654541, 4.303954601287842, 3.148632049560547, 2.4550487995147705, 2.9045116901397705, 3.1866486072540283, 3.1447479724884033, 3.9929845333099365, 3.745150566101074, 3.1003527641296387, 2.7118194103240967, 2.188410758972168, 4.482717514038086, 4.361356735229492, 2.5309271812438965, 3.243727445602417, 2.37420654296875, 4.4033427238464355, 2.5346782207489014, 3.033007860183716, 2.270538091659546, 2.1237597465515137, 3.563248872756958, 4.434279918670654, 3.805985689163208, 2.956608295440674, 3.8031163215637207, 4.038758277893066, 3.1751484870910645, 3.9535393714904785, 2.306133270263672, 3.0066444873809814, 3.510167360305786, 3.649400472640991, 2.638126850128174, 2.481135845184326, 2.14772367477417, 3.2737367153167725, 3.541820526123047, 3.6085362434387207, 3.457249164581299, 3.9423625469207764, 3.80584716796875, 2.3756964206695557, 1.9246306419372559, 3.976283073425293, 2.126735210418701, 3.607205629348755, 2.9521584510803223, 2.3646597862243652, 2.736316442489624, 2.8538975715637207, 2.314112901687622, 2.5715794563293457, 3.127028703689575, 3.7432994842529297, 3.166429281234741, 2.9879367351531982, 4.6511335372924805, 4.124600887298584, 2.9855563640594482, 3.447282075881958, 2.773416042327881, 2.8118367195129395, 5.475109100341797, 3.7407519817352295, 3.9193224906921387, 3.1347973346710205, 2.7095189094543457, 3.1750688552856445, 3.883578300476074, 3.8101704120635986, 3.4312925338745117, 3.381974458694458, 2.1485540866851807, 3.943476438522339, 2.815934896469116, 4.188860893249512, 3.840101957321167, 4.037944793701172, 5.082420825958252, 3.3461010456085205, 3.536808490753174, 4.736212253570557, 3.172276020050049, 1.7334234714508057, 4.10923433303833, 3.939227819442749, 2.3794336318969727, 2.556169033050537, 3.275291919708252, 2.3635013103485107, 3.4402341842651367, 3.332247257232666, 2.646052122116089, 2.160273790359497, 2.062502384185791, 3.410081624984741, 4.097565650939941, 4.76313591003418, 4.631088733673096, 1.98717200756073, 5.206784725189209, 3.7845981121063232, 2.2410717010498047, 2.654264450073242, 3.3001537322998047, 4.351809501647949, 2.367144823074341, 3.028113603591919, 3.497471332550049, 2.4940669536590576, 4.019257545471191, 2.5907225608825684, 3.7560620307922363, 2.427631378173828, 4.696995735168457, 3.792855978012085, 2.8971481323242188, 4.416199684143066, 2.2619504928588867, 2.931065082550049, 3.3886897563934326, 3.247513771057129, 104.45099639892578, 198.2548828125, 100.986328125, 205.9917755126953, 64.58501434326172, 608.390380859375, 131.978271484375, 60.6309814453125, 46.76361083984375, 178.70530700683594, 374.56573486328125, 342.3224792480469, 267.687255859375, 266.1087951660156, 433.5381164550781, 176.12034606933594, 78.06034851074219, 206.4657745361328, 56.32757568359375, 495.492919921875, 102.94501495361328, 211.58457946777344, 315.56365966796875, 430.40771484375, 98.15827941894531, 186.6697998046875, 181.65362548828125, 203.16168212890625, 321.8019714355469, 139.4795684814453, 51.41523742675781, 169.4998779296875, 624.6973266601562, 119.841796875, 237.8709259033203, 195.2469482421875, 129.970458984375, 50.50031280517578, 107.2137451171875, 272.3324279785156, 440.4584655761719, 408.4462890625, 316.192138671875, 294.9395751953125, 221.84835815429688, 478.4696350097656, 136.67474365234375, 230.3796844482422, 103.04959106445312, 239.37559509277344, 243.3856201171875, 185.7664337158203, 404.4283447265625, 140.4320831298828, 171.11380004882812, 213.55003356933594, 67.9322509765625, 107.87430572509766, 268.9341125488281, 314.5559997558594, 188.92507934570312, 205.1356964111328, 171.903076171875, 132.7893829345703, 270.87115478515625, 302.71295166015625, 240.6161651611328, 362.9366760253906, 281.9267272949219, 100.94068145751953, 74.88162231445312, 146.93170166015625, 191.681396484375, 62.29201126098633, 699.1461791992188, 274.614990234375, 378.930419921875, 93.6280517578125, 232.69677734375, 193.00991821289062, 504.96044921875, 612.1119384765625, 693.6472778320312, 344.5353088378906, 93.74073028564453, 398.9136657714844, 434.9684143066406, 474.20263671875, 299.3427734375, 327.2597351074219, 139.543212890625, 136.503662109375, 97.23531341552734, 319.7785339355469, 249.11643981933594, 83.62281036376953, 496.9894714355469, 198.8927764892578, 289.657958984375, 176.96218872070312, 248.6695098876953, 124.97503662109375, 119.71894073486328, 345.7590026855469, 190.2974395751953, 230.41026306152344, 62.46297836303711, 313.25738525390625, 166.54652404785156, 111.04370880126953, 510.15045166015625, 243.04417419433594, 106.37835693359375, 344.13739013671875, 202.651123046875, 199.03762817382812, 152.12054443359375, 203.9154815673828, 81.12154388427734, 208.91278076171875, 75.21722412109375, 479.0322265625, 199.8595733642578, 202.49639892578125, 410.8595275878906, 198.30416870117188, 270.4503173828125, 280.91998291015625, 127.22832489013672, 339.4939270019531, 390.9061584472656, 605.2836303710938, 124.29144287109375, 210.1844482421875, 173.61767578125, 407.5592041015625, 174.32763671875, 280.8546142578125, 181.78460693359375, 186.99221801757812, 240.94921875, 353.4347229003906, 160.1766357421875, 376.2616271972656, 378.111328125, 138.22698974609375, 338.6695251464844, 94.3644027709961, 108.35344696044922, 180.4443359375, 196.84776306152344, 248.66302490234375, 309.2145080566406, 500.6759948730469, 153.552490234375, 317.21209716796875, 171.7450408935547, 629.3045043945312, 79.7777099609375, 273.1800842285156, 87.79093933105469, 456.42864990234375, 128.427001953125, 313.60321044921875, 280.8659973144531, 339.73895263671875, 226.52978515625, 396.81195068359375, 178.47042846679688, 113.23999786376953, 401.5889892578125, 268.3109130859375, 101.08184051513672, 313.4532470703125, 414.35858154296875, 470.9751892089844, 302.6922607421875, 102.93468475341797, 320.489013671875, 217.63015747070312, 291.2209167480469, 196.5809326171875, 445.6600646972656, 106.28394317626953, 373.564453125, 205.3050537109375, 233.86453247070312, 80.80474090576172, 339.7974853515625, 501.3121643066406, 378.9344177246094, 439.7108154296875, 128.1044921875, 157.0411834716797, 127.149658203125, 382.7361755371094, 290.7122802734375, 568.181640625, 283.8717041015625, 275.28564453125, 531.6337890625, 446.0890808105469, 71.7689437866211, 577.8749389648438, 371.1793518066406, 97.69950866699219, 91.56476593017578, 83.55665588378906, 200.10513305664062, 54.670536041259766, 226.73538208007812, 105.76612854003906, 77.06993103027344, 109.74476623535156, 324.70947265625, 370.9501037597656, 70.69927215576172, 216.77053833007812, 208.4940948486328, 621.9863891601562, 94.302001953125, 45.64075469970703, 291.0780944824219, 85.44438934326172, 258.0722961425781, 259.56890869140625, 87.63750457763672, 261.01806640625, 363.4705505371094, 285.7515869140625, 97.07875061035156, 153.60943603515625, 130.77447509765625, 215.26800537109375, 285.2947082519531, 449.3388671875, 125.2635498046875, 357.41162109375, 105.431884765625, 828.6121826171875, 397.742919921875, 231.73167419433594, 236.53192138671875, 71.88312530517578, 131.49761962890625, 161.5863494873047, 238.57083129882812, 194.0935516357422, 326.7901611328125, 367.01763916015625, 207.61924743652344, 201.7565460205078, 92.041748046875, 464.020263671875, 156.58099365234375, 80.7750473022461, 224.61000061035156, 308.2937316894531, 354.74041748046875, 276.5400390625, 219.71722412109375, 187.32891845703125, 231.64508056640625, 270.7388916015625, 122.93242645263672, 127.07781219482422, 60.04153060913086, 177.25927734375, 156.55792236328125, 93.85218811035156, 308.23193359375, 97.155029296875, 85.50548553466797, 399.5914611816406, 348.3836364746094, 207.79901123046875, 204.1637725830078, 173.7948455810547, 221.96173095703125, 111.23990631103516, 131.89366149902344, 118.85948944091797, 226.1122589111328, 356.9618225097656, 455.8049011230469, 401.678466796875, 470.4900817871094, 326.23004150390625, 180.19827270507812, 180.7528839111328, 208.26820373535156, 459.2235107421875, 203.17974853515625, 90.62818908691406, 82.72443389892578, 74.8055419921875, 49.886962890625, 310.3511962890625, 509.8774108886719, 137.397705078125, 3.7542529106140137, 2.7663238048553467, 3.1133065223693848, 1.5864349603652954, 3.8069028854370117, 2.5903408527374268, 4.026910305023193, 1.6598016023635864, 4.121336460113525, 2.042520046234131, 2.151184320449829, 2.9106602668762207, 2.918616533279419, 2.5330591201782227, 1.6967432498931885, 3.0475053787231445, 2.8174357414245605, 3.004389524459839, 1.6017179489135742, 1.3903058767318726, 1.811299204826355, 2.5187506675720215, 1.9403334856033325, 2.7801735401153564, 3.146596670150757, 3.4534547328948975, 1.8824491500854492, 2.171801805496216, 3.1727311611175537, 2.901719331741333, 2.2079076766967773, 3.6060760021209717, 2.1919429302215576, 3.2742226123809814, 3.845950126647949, 2.429636240005493, 3.5420825481414795, 2.2219078540802, 2.7998034954071045, 4.108871936798096, 1.273842453956604, 3.548098564147949, 2.597560405731201, 2.9185791015625, 3.6951305866241455, 2.5184102058410645, 2.8933162689208984, 2.141970634460449, 1.6919834613800049, 1.8188533782958984, 2.6511547565460205, 3.5996651649475098, 2.562605857849121, 2.698167085647583, 3.427382707595825, 3.087150812149048, 2.332882881164551, 2.2987256050109863, 2.0197479724884033, 3.4108667373657227, 2.0304975509643555, 1.6720778942108154, 2.348590135574341, 2.0988707542419434, 3.6659421920776367, 3.365659475326538, 2.6177358627319336, 2.0039753913879395, 2.736285924911499, 1.6006792783737183, 2.446538209915161, 3.0130605697631836, 3.1536340713500977, 2.692272901535034, 3.1692326068878174, 4.08488655090332, 3.7243528366088867, 2.492886543273926, 1.3825081586837769, 1.7483129501342773, 2.9061760902404785, 2.0006566047668457, 1.750142216682434, 3.8451647758483887, 2.2004637718200684, 2.686431884765625, 2.4775819778442383, 2.6250762939453125, 3.2182493209838867, 2.5709428787231445, 2.9538891315460205, 3.1821508407592773, 2.410458564758301, 1.7693527936935425, 2.503476142883301, 3.3874828815460205, 3.915905714035034, 2.8980565071105957, 2.2148501873016357, 2.7582902908325195, 3.226107597351074, 1.568587303161621, 3.26340389251709, 3.312106132507324, 2.014779567718506, 1.930886149406433, 2.899592161178589, 3.703933000564575, 3.4788177013397217, 2.0822908878326416, 2.745467185974121, 3.1279382705688477, 2.416213035583496, 2.9181759357452393, 1.2236783504486084, 3.7759664058685303, 2.4931247234344482, 3.0769174098968506, 3.416335344314575, 1.7018805742263794, 2.6202964782714844, 2.769627332687378, 1.400383710861206, 3.328678607940674, 2.0065650939941406, 3.0839359760284424, 2.555981397628784, 3.1649084091186523, 2.7297258377075195, 1.9019825458526611, 3.5656731128692627, 2.721466541290283, 3.7110490798950195, 2.6966664791107178, 3.9300944805145264, 2.9611332416534424, 2.73105525970459, 3.211613655090332, 2.7833666801452637, 3.194547653198242, 1.9092206954956055, 2.063934803009033, 1.585614800453186, 4.588135719299316, 1.9862573146820068, 3.8846867084503174, 2.2889151573181152, 3.8395814895629883, 3.938833475112915, 2.535763740539551, 2.275805950164795, 2.005126953125, 2.712841749191284, 2.6883673667907715, 3.1758689880371094, 2.7986364364624023, 3.2460484504699707, 2.5624194145202637, 4.335859775543213, 1.7781685590744019, 2.991111993789673, 2.05078387260437, 2.6810390949249268, 3.0895793437957764, 3.3973605632781982, 1.8209506273269653, 2.269820213317871, 2.945613384246826, 2.849564790725708, 3.167996644973755, 3.6749355792999268, 2.462907552719116, 1.9607058763504028, 1.5686681270599365, 3.3797295093536377, 3.047624349594116, 2.6179211139678955, 1.5473183393478394, 2.168431282043457, 1.749018669128418, 2.942814826965332, 3.986370801925659, 1.945820927619934, 2.4371354579925537, 1.9740341901779175, 3.1472346782684326, 3.788602113723755, 3.7190380096435547, 2.6710143089294434, 1.784729242324829, 2.749102830886841, 2.444716453552246, 2.055760383605957, 1.9262800216674805, 2.578112840652466, 1.243630290031433, 3.303723096847534, 3.0441360473632812, 2.6067464351654053, 1.9238882064819336, 3.175403118133545, 4.1113200187683105, 2.7334892749786377, 2.714312791824341, 2.0421338081359863, 2.5805792808532715, 3.68851375579834, 2.656663179397583, 2.2002077102661133, 3.5415356159210205, 2.3368124961853027, 2.9089250564575195, 1.8194150924682617, 3.151654005050659, 3.7986254692077637, 1.770622968673706, 2.935154914855957, 2.7151119709014893, 1.9306036233901978, 3.472801446914673, 2.285508632659912, 1.8037904500961304, 2.828760862350464, 2.220452308654785, 2.842632293701172, 3.0222675800323486, 2.0928430557250977, 3.995958089828491, 2.3285276889801025, 2.883831739425659, 2.9896020889282227, 1.9542760848999023, 3.096024751663208, 2.2190935611724854, 2.8217830657958984, 2.713202476501465, 2.157965660095215, 2.2349143028259277, 2.078263282775879, 2.6191723346710205, 2.298943519592285, 2.9704034328460693, 2.292322874069214, 2.303410530090332, 2.045469045639038, 2.7802562713623047, 1.3641244173049927, 2.9790942668914795, 1.9118306636810303, 2.0831139087677, 2.2017030715942383, 2.6230883598327637, 2.6246461868286133, 3.012944221496582, 3.8233447074890137, 2.5733349323272705, 2.951347589492798, 2.519439220428467, 2.8200523853302, 1.4668989181518555, 3.9506382942199707, 2.3025693893432617, 2.8051562309265137, 3.744328498840332, 2.5530548095703125, 1.5658565759658813, 2.3700857162475586, 3.1294848918914795, 2.902665376663208, 2.622291088104248, 2.5912792682647705, 2.730189800262451, 2.6436564922332764, 1.5406731367111206, 2.639693021774292, 3.413456678390503, 2.297640562057495, 1.97798752784729, 2.8471667766571045, 2.602677583694458, 2.3419692516326904, 2.206179618835449, 2.3385438919067383, 3.4418628215789795, 3.6296818256378174, 1.6034365892410278, 3.1309075355529785, 2.638688325881958, 2.959527015686035, 2.8657445907592773, 2.7642815113067627, 3.680079936981201, 3.792205810546875, 2.2531046867370605, 2.41878604888916, 2.0856714248657227, 1.59103262424469, 2.5621349811553955, 2.1090927124023438, 2.1435458660125732, 0.2951774597167969, 0.22950057685375214, 0.23876380920410156, 0.29363495111465454, 0.21472689509391785, 0.3029368817806244, 0.24664589762687683, 0.23338381946086884, 0.3401947617530823, 0.24908499419689178, 0.3073532283306122, 0.21361030638217926, 0.26807311177253723, 0.2374013215303421, 0.25590065121650696, 0.2978217899799347, 0.21463802456855774, 0.21713787317276, 0.305204302072525, 0.2619496285915375, 0.28500017523765564, 0.287252813577652, 0.24957618117332458, 0.24049967527389526, 0.29524165391921997, 0.24405452609062195, 0.3283582329750061, 0.17263250052928925, 0.2763001322746277, 0.28978633880615234, 0.22869274020195007, 0.30439844727516174, 0.24074772000312805, 0.30260276794433594, 0.25882983207702637, 0.34538039565086365, 0.21575187146663666, 0.2248287796974182, 0.256597638130188, 0.2509256601333618, 0.20539939403533936, 0.2673231363296509, 0.2846660315990448, 0.23446866869926453, 0.2924412786960602, 0.25700125098228455, 0.1959427148103714, 0.2956691086292267, 0.17389218509197235, 0.20577697455883026, 0.2385108321905136, 0.2730455994606018, 0.24064788222312927, 0.32189443707466125, 0.30206528306007385, 0.25285178422927856, 0.2134099006652832, 0.20885390043258667, 0.2685733735561371, 0.26503515243530273, 0.144623264670372, 0.28469547629356384, 0.2532925009727478, 0.28338927030563354, 0.3348013162612915, 0.24819748103618622, 0.29128262400627136, 0.2718053460121155, 0.2855599522590637, 0.21683089435100555, 0.27545103430747986, 0.21547354757785797, 0.29705512523651123, 0.2579757571220398, 0.27812492847442627, 0.24625998735427856, 0.24379684031009674, 0.23988734185695648, 0.2531437277793884, 0.2616000175476074, 0.25077396631240845, 0.23420070111751556, 0.22758716344833374, 0.2822341024875641, 0.22319075465202332, 0.19407042860984802, 0.2816499173641205, 0.26903170347213745, 0.26407432556152344, 0.26429054141044617, 0.2441851794719696, 0.2762208580970764, 0.25186794996261597, 0.23151296377182007, 0.30527156591415405, 0.2959517240524292, 0.24282275140285492, 0.2971845865249634, 0.28356221318244934, 0.2947085201740265, 0.3091218173503876, 0.2082708328962326, 0.290139377117157, 0.2651005983352661, 0.26584428548812866, 0.24232523143291473, 0.24103419482707977, 0.28464895486831665, 0.24530012905597687, 0.2820521593093872, 0.2410355657339096, 0.22184598445892334, 0.23905986547470093, 0.23648330569267273, 0.24736367166042328, 0.22158189117908478, 0.29629382491111755, 0.31699636578559875, 0.2606147825717926, 0.2498948574066162, 0.248508483171463, 0.30607742071151733, 0.28610220551490784, 0.2845050096511841, 0.2438337653875351, 0.26492998003959656, 0.2683736979961395, 0.27281415462493896, 0.2103303074836731, 0.1812140941619873, 0.2850264608860016, 0.24832651019096375, 0.29246920347213745, 0.2707981467247009, 0.26573920249938965, 0.1927727311849594, 0.24682287871837616, 0.2535575330257416, 0.25769880414009094, 0.26531901955604553, 0.28987985849380493, 0.3287911117076874, 0.25803709030151367, 0.23647622764110565, 0.19373664259910583, 0.26367300748825073, 0.2837369740009308, 0.27528223395347595, 0.2710514962673187, 0.27482420206069946, 0.2589571475982666, 0.25400304794311523, 0.2661741077899933, 0.2960495948791504, 0.18353305757045746, 0.2783297300338745, 0.24971003830432892, 0.26309898495674133, 0.28269490599632263, 0.26540452241897583, 0.34547606110572815, 0.21397870779037476, 0.28705906867980957, 0.2961083650588989, 0.2589625120162964, 0.3202558159828186, 0.2227189987897873, 0.2999403774738312, 0.29546117782592773, 0.2272815704345703, 0.2088225930929184, 0.2966291010379791, 0.25060126185417175, 0.22892121970653534, 0.28960758447647095, 0.28356727957725525, 0.28340521454811096, 0.2594449818134308, 0.25323861837387085, 0.2503662705421448, 0.21517129242420197, 0.25412440299987793, 0.2981286644935608, 0.2573290169239044, 0.3201453387737274, 0.2684619128704071, 0.21141117811203003, 0.273955374956131, 0.20373591780662537, 0.28857657313346863, 0.25825026631355286, 0.2887694537639618, 0.24309809505939484, 0.28916794061660767, 0.3485359847545624, 0.2508256435394287, 0.20013558864593506, 0.2618611752986908, 0.2626965045928955, 0.28361427783966064, 0.18904781341552734, 0.2503967583179474, 0.28722721338272095, 0.2892676591873169, 0.23091521859169006, 0.3111785054206848, 0.29308879375457764, 0.2827771008014679, 0.18691463768482208, 0.2636570632457733, 0.25982266664505005, 0.2740837335586548, 0.2822745442390442, 0.2977733612060547, 0.2406824231147766, 0.28514575958251953, 0.19495688378810883, 0.22097425162792206, 0.278622031211853, 0.3208731412887573, 0.2679133117198944, 0.3347168564796448, 0.21027785539627075, 0.19116809964179993, 0.2467166781425476, 0.2526940405368805, 0.2787536084651947, 0.2513575553894043, 0.2836376428604126, 0.24097007513046265, 0.24477039277553558, 0.23041175305843353, 0.24509429931640625, 0.24901437759399414, 0.29471534490585327, 0.23925244808197021, 0.2705044150352478, 0.24752961099147797, 0.3119209110736847, 0.2446126937866211, 0.2646089196205139, 0.2776937186717987, 0.24290618300437927, 0.24593539535999298, 0.22795331478118896, 0.23523932695388794, 0.2439984530210495, 0.19617435336112976, 0.34472164511680603, 0.20580798387527466, 0.2592514157295227, 0.31937605142593384, 0.22816485166549683, 0.24166761338710785, 0.266672283411026, 0.24621817469596863, 0.24982032179832458, 0.29806095361709595, 0.2346924990415573, 0.250750869512558, 0.22756536304950714, 0.2195386290550232, 0.2443297952413559, 0.243644118309021, 0.3077734708786011, 0.264473557472229, 0.30881232023239136, 0.2136090099811554, 0.26647213101387024, 0.26275473833084106, 0.29671865701675415, 0.2467208057641983, 0.2577812373638153, 0.25555893778800964, 0.2275686264038086, 0.3196372389793396, 0.30953577160835266, 0.1963958740234375, 0.24608489871025085, 0.2751474678516388, 0.2553691864013672, 0.25474727153778076, 0.25513049960136414, 0.3033611476421356, 0.2303711324930191, 0.2936630845069885, 0.26886823773384094, 0.3038172125816345, 0.2300814539194107, 0.266796350479126, 0.2669791281223297, 0.2963525354862213, 0.23485320806503296, 0.22781550884246826, 0.26357460021972656, 0.29059675335884094, 0.25236985087394714, 0.2888298034667969, 0.18225927650928497, 0.21903394162654877, 3.9010612964630127, 3.31445050239563, 4.627964496612549, 2.652348518371582, 2.5836098194122314, 2.7249209880828857, 2.6600115299224854, 3.707371234893799, 2.7037289142608643, 2.568082332611084, 2.767897367477417, 4.64630126953125, 2.875413656234741, 2.3894872665405273, 3.3653106689453125, 2.097614049911499, 3.101109504699707, 3.646550416946411, 3.532299757003784, 2.3788745403289795, 3.927858829498291, 4.680051803588867, 2.613900661468506, 4.272157669067383, 3.586801767349243, 2.6621434688568115, 3.505671977996826, 3.6717023849487305, 3.930845260620117, 3.939608097076416, 3.0639283657073975, 2.4067232608795166, 3.246201753616333, 3.288433790206909, 3.717890501022339, 2.4743142127990723, 2.819671630859375, 3.2399778366088867, 3.039656400680542, 2.901089906692505, 2.2124900817871094, 2.033484697341919, 2.8005752563476562, 3.5242607593536377, 3.583935499191284, 2.992954730987549, 2.4848415851593018, 3.0436906814575195, 3.534442663192749, 3.763279914855957, 2.776186466217041, 3.6853578090667725, 3.069786548614502, 1.8851999044418335, 3.601919174194336, 2.825000047683716, 2.7156999111175537, 3.26751446723938, 3.406548500061035, 2.3765869140625, 3.8056445121765137, 2.8300087451934814, 2.920910596847534, 4.5297322273254395, 2.975177526473999, 2.574078321456909, 3.5954015254974365, 3.430227279663086, 4.646378517150879, 2.528071403503418, 3.027688503265381, 3.206514835357666, 2.3420987129211426, 1.9714998006820679, 4.453886032104492, 3.748568534851074, 2.334507465362549, 3.0456695556640625, 3.310852527618408, 3.1538727283477783, 2.914745330810547, 3.0188546180725098, 3.8779149055480957, 3.9053075313568115, 2.7506377696990967, 2.9111409187316895, 2.8625969886779785, 4.909675598144531, 2.3389906883239746, 4.212625503540039, 3.8522143363952637, 3.6085948944091797, 3.681521415710449, 3.0976550579071045, 3.5895068645477295, 5.033016204833984, 3.3290672302246094, 2.598193407058716, 2.999556303024292, 1.98634672164917, 2.7013275623321533, 2.9004006385803223, 4.148890495300293, 3.1303417682647705, 2.396176338195801, 2.9046120643615723, 3.9573159217834473, 3.350177526473999, 3.931995153427124, 3.759721040725708, 4.043224334716797, 3.4776198863983154, 3.5733234882354736, 4.388054847717285, 3.5215649604797363, 3.839348077774048, 2.992361307144165, 4.081021785736084, 3.4654088020324707, 2.652158260345459, 3.531230926513672, 3.3555009365081787, 2.824115514755249, 3.659616231918335, 4.769306659698486, 3.3551430702209473, 2.1229031085968018, 3.144533634185791, 3.22355580329895, 2.3557374477386475, 3.345919132232666, 4.299629211425781, 3.0029613971710205, 3.7174878120422363, 3.0368919372558594, 4.420300006866455, 4.254237174987793, 2.9545605182647705, 4.031959533691406, 4.073541641235352, 2.1704981327056885, 3.81526255607605, 3.544856548309326, 3.896327495574951, 3.2796146869659424, 2.373751401901245, 3.338261127471924, 4.7752509117126465, 3.285597562789917, 2.103577136993408, 4.3010382652282715, 3.788875102996826, 3.892174482345581, 1.9601598978042603, 3.7330944538116455, 2.6322357654571533, 3.2352089881896973, 3.3402397632598877, 2.5286805629730225, 4.176252841949463, 3.8485913276672363, 3.0464565753936768, 3.332054615020752, 3.6072838306427, 3.109898090362549, 3.4889144897460938, 3.6938540935516357, 1.8952795267105103, 2.9753758907318115, 4.313163757324219, 2.9232475757598877, 3.03025221824646, 2.722209930419922, 2.5315637588500977, 4.008105754852295, 3.4407958984375, 3.3890926837921143, 2.5463619232177734, 2.466829538345337, 3.965806722640991, 3.4840309619903564, 3.851067066192627, 4.180825233459473, 3.3436155319213867, 3.428410530090332, 3.570467948913574, 3.1934754848480225, 3.2568840980529785, 4.2469000816345215, 2.4766464233398438, 3.05999755859375, 2.453617811203003, 4.481740951538086, 4.812718868255615, 3.0203118324279785, 2.216139793395996, 3.0959858894348145, 4.028820037841797, 3.0755867958068848, 4.118703365325928, 3.384904146194458, 3.1036148071289062, 1.8826384544372559, 3.3895103931427, 2.2282824516296387, 2.9125847816467285, 3.1523971557617188, 1.6669082641601562, 3.663180351257324, 2.6439013481140137, 3.0818188190460205, 4.575561046600342, 2.254558801651001, 3.2710766792297363, 2.445509672164917, 2.539461612701416, 2.8740248680114746, 3.1470401287078857, 2.960843324661255, 2.975728750228882, 3.504897356033325, 2.3138060569763184, 3.5870115756988525, 4.057950973510742, 3.71463942527771, 3.9598329067230225, 2.251018762588501, 2.914945602416992, 2.8204140663146973, 2.9468472003936768, 2.0366339683532715, 2.7767224311828613, 3.6161930561065674, 3.701082468032837, 4.621162414550781, 3.015995502471924, 3.353151798248291, 4.049886226654053, 4.475584030151367, 3.4546995162963867, 3.409355640411377, 3.3699986934661865, 3.4154582023620605, 2.1485724449157715, 3.244889497756958, 2.5764660835266113, 3.6375179290771484, 2.186342716217041, 3.544964551925659, 2.584196090698242, 4.263016223907471, 2.3152318000793457, 2.5164549350738525, 2.849480628967285, 3.320516586303711, 3.9091148376464844, 4.180529594421387, 3.6734189987182617, 3.2574353218078613, 3.3040401935577393, 4.381738662719727, 3.7998008728027344, 2.3731040954589844, 4.931333065032959, 2.4166903495788574, 4.158541679382324, 3.9014995098114014, 2.5140647888183594, 4.342487812042236, 2.892850875854492, 2.3625504970550537, 3.1800129413604736, 2.8917622566223145, 3.7651469707489014, 3.068840980529785, 3.5164482593536377, 2.870561361312866, 2.6122798919677734, 2.3594164848327637, 2.910372495651245, 3.100891590118408, 1.813496470451355, 3.7362446784973145, 2.911220073699951, 2.7290685176849365, 2.5444629192352295, 3.7851791381835938, 2.9550769329071045, 1.9906896352767944, 3.7249913215637207, 2.8377490043640137, 3.970609664916992, 3.302217960357666, 4.5594482421875, 2.954540967941284, 4.049117565155029, 5.254081726074219, 3.0208466053009033, 2.6639862060546875, 3.961238384246826, 532.6832885742188, 641.3370361328125, 226.07485961914062, 457.6890563964844, 482.3485412597656, 140.98382568359375, 357.857421875, 136.78887939453125, 156.83935546875, 105.1805419921875, 408.4757995605469, 385.13507080078125, 80.13284301757812, 78.2875747680664, 501.7645568847656, 74.76278686523438, 217.6953887939453, 92.7098159790039, 502.1964416503906, 235.0096435546875, 116.41033935546875, 481.83428955078125, 145.66854858398438, 349.7958984375, 324.141357421875, 191.052490234375, 340.0984191894531, 80.92835235595703, 605.22265625, 150.0021209716797, 626.7877807617188, 95.563232421875, 115.07613372802734, 126.80254364013672, 330.044921875, 294.5340881347656, 139.95166015625, 77.18161010742188, 304.8810729980469, 451.7767333984375, 163.28402709960938, 428.6678771972656, 393.9288330078125, 164.42803955078125, 129.86793518066406, 126.17272186279297, 120.65727996826172, 310.00439453125, 545.7325439453125, 188.71246337890625, 170.401611328125, 104.76132202148438, 147.60305786132812, 228.82275390625, 301.1534423828125, 119.93193817138672, 202.64480590820312, 235.9139404296875, 331.7899169921875, 455.2555236816406, 210.90394592285156, 250.53427124023438, 181.15521240234375, 335.38690185546875, 96.2215576171875, 335.6490478515625, 398.29339599609375, 213.77227783203125, 568.4223022460938, 199.0902557373047, 197.76585388183594, 154.2830810546875, 352.8028869628906, 385.3648376464844, 162.33642578125, 342.6087951660156, 527.9698486328125, 166.9907989501953, 89.79054260253906, 91.27864837646484, 84.0057373046875, 150.98098754882812, 218.4580078125, 237.7456817626953, 415.344482421875, 319.88433837890625, 136.92974853515625, 85.9656982421875, 301.5013732910156, 288.523193359375, 296.2795715332031, 361.3976745605469, 71.81561279296875, 132.28379821777344, 506.7164611816406, 385.26513671875, 141.5175018310547, 450.8371276855469, 346.01617431640625, 136.91534423828125, 437.4012451171875, 191.0877227783203, 133.87060546875, 304.24517822265625, 427.458984375, 200.596923828125, 206.0904083251953, 202.4881134033203, 454.3978271484375, 92.96185302734375, 255.03662109375, 238.8238067626953, 100.52812957763672, 114.82421875, 120.284912109375, 116.15447998046875, 110.20372772216797, 194.84152221679688, 56.412410736083984, 375.6017150878906, 128.86419677734375, 554.90771484375, 211.69107055664062, 226.56581115722656, 586.04052734375, 112.45246887207031, 252.83566284179688, 212.50991821289062, 383.2763671875, 426.5633544921875, 378.5486755371094, 200.3299102783203, 57.987850189208984, 201.70071411132812, 274.9267272949219, 300.0347900390625, 67.18605041503906, 462.6170959472656, 195.0130615234375, 403.039794921875, 418.8143005371094, 189.71885681152344, 77.85112762451172, 140.0741424560547, 441.1698303222656, 127.791259765625, 259.23773193359375, 151.78651428222656, 118.538818359375, 181.7861328125, 500.7645568847656, 209.24278259277344, 196.50901794433594, 261.5211181640625, 178.4636688232422, 430.80413818359375, 85.58856964111328, 171.21957397460938, 326.4248046875, 150.76171875, 172.6962890625, 315.85003662109375, 142.17164611816406, 449.28912353515625, 121.66509246826172, 200.45237731933594, 275.00537109375, 599.2514038085938, 258.98370361328125, 417.0472412109375, 221.89280700683594, 579.6805419921875, 155.48477172851562, 225.7845458984375, 667.2118530273438, 186.68753051757812, 134.62921142578125, 389.68310546875, 146.70762634277344, 174.96202087402344, 177.49668884277344, 337.9510803222656, 326.3671875, 267.4525146484375, 165.67913818359375, 80.36224365234375, 157.67633056640625, 431.5692443847656, 86.74822998046875, 91.3697280883789, 270.3001708984375, 151.49986267089844, 253.83740234375, 128.84295654296875, 310.2532043457031, 487.0865478515625, 305.3196716308594, 72.19707489013672, 159.0731201171875, 309.8390197753906, 169.2322998046875, 166.5614471435547, 200.05577087402344, 334.2828063964844, 229.77099609375, 340.234375, 175.8963623046875, 464.097412109375, 316.3275146484375, 213.98741149902344, 545.9677734375, 168.80133056640625, 332.4002990722656, 425.2255859375, 296.8460998535156, 81.48646545410156, 191.45030212402344, 193.0077362060547, 386.2384338378906, 614.1514282226562, 150.5456085205078, 623.9281616210938, 191.9541015625, 232.28143310546875, 159.2327880859375, 185.08763122558594, 485.3953552246094, 144.791259765625, 516.8125, 409.37646484375, 308.5426940917969, 150.34043884277344, 346.11749267578125, 554.4615478515625, 127.90370178222656, 263.36767578125, 369.8258361816406, 258.5531311035156, 60.523738861083984, 460.1336975097656, 240.5322265625, 210.6612091064453, 574.5105590820312, 146.90185546875, 154.0626678466797, 122.047607421875, 162.79266357421875, 211.77171325683594, 138.74082946777344, 208.86636352539062, 212.2323760986328, 434.5902099609375, 205.3993377685547, 60.317771911621094, 149.63339233398438, 265.2476806640625, 75.18939971923828, 435.8514099121094, 509.3515625, 255.00515747070312, 244.99102783203125, 129.744384765625, 148.61001586914062, 326.16839599609375, 283.1865234375, 349.3603515625, 605.9418334960938, 469.1783447265625, 217.49026489257812, 120.55909729003906, 57.590576171875, 103.90265655517578, 341.68035888671875, 255.82823181152344, 551.4365234375, 477.5356140136719, 89.22674560546875, 316.0355224609375, 143.0656280517578, 236.20277404785156, 311.89990234375, 165.150390625, 217.0238037109375, 334.6011657714844, 214.2185516357422, 242.3749542236328, 224.5609130859375, 322.7202453613281, 158.26007080078125, 356.64202880859375, 134.674072265625, 529.2529296875, 209.9857177734375, 231.49261474609375, 267.0251770019531, 240.9736328125, 258.1581115722656, 96.87525939941406, 297.72015380859375, 303.66796875, 2.1839723587036133, 4.187607765197754, 2.1249213218688965, 3.0486271381378174, 2.4616339206695557, 2.547003746032715, 2.090662956237793, 3.799586772918701, 3.0116608142852783, 3.0951855182647705, 3.534214973449707, 3.7972233295440674, 3.092902183532715, 3.824894905090332, 1.716150164604187, 3.487665891647339, 2.5103342533111572, 3.061296224594116, 2.168816566467285, 3.109281539916992, 2.3645219802856445, 1.5545806884765625, 2.6162211894989014, 2.7530853748321533, 2.3461313247680664, 3.7944958209991455, 3.728821277618408, 3.620551109313965, 2.4729983806610107, 3.9136576652526855, 3.363063335418701, 3.057018995285034, 2.2823851108551025, 2.635321617126465, 2.4227867126464844, 2.050525426864624, 2.5189714431762695, 2.3218257427215576, 1.7253568172454834, 2.4180543422698975, 2.4799985885620117, 2.534867286682129, 3.539760112762451, 1.7245455980300903, 2.8469340801239014, 2.9882023334503174, 2.165158271789551, 3.4321582317352295, 1.6931126117706299, 3.094080686569214, 2.298333168029785, 2.13879132270813, 2.40708589553833, 3.2223503589630127, 1.6103074550628662, 2.805723190307617, 1.8397212028503418, 2.799891233444214, 1.9606297016143799, 3.972090482711792, 3.8514244556427, 3.4879372119903564, 2.922422170639038, 2.8759047985076904, 3.1478307247161865, 3.331088066101074, 2.2899088859558105, 3.346907377243042, 1.729243278503418, 3.5298662185668945, 3.283470630645752, 2.7820351123809814, 1.7688583135604858, 2.914412498474121, 2.0338919162750244, 2.551814556121826, 1.6379599571228027, 1.8050768375396729, 1.4649955034255981, 2.043259620666504, 2.2338972091674805, 2.6844584941864014, 3.0411627292633057, 2.004375457763672, 2.5360119342803955, 1.3059014081954956, 1.5505174398422241, 1.8311394453048706, 2.2254438400268555, 2.6772701740264893, 2.7537930011749268, 2.702130079269409, 3.010350227355957, 3.4399614334106445, 1.63568115234375, 2.9047787189483643, 3.0368645191192627, 3.100006341934204, 2.155531644821167, 1.779552936553955, 1.9956728219985962, 2.7088394165039062, 3.8018789291381836, 3.6129672527313232, 1.9664925336837769, 1.7718021869659424, 3.618886947631836, 2.7295982837677, 3.53472638130188, 1.5131587982177734, 3.0760257244110107, 3.699460029602051, 2.5723445415496826, 3.417322874069214, 2.610549211502075, 2.292497158050537, 3.282953977584839, 2.0751891136169434, 2.7789909839630127, 2.407397747039795, 3.886550188064575, 3.3490283489227295, 2.378363609313965, 3.5433263778686523, 2.599231004714966, 1.9576548337936401, 2.0034894943237305, 2.321150779724121, 2.836580753326416, 2.7059056758880615, 3.0548412799835205, 3.0117580890655518, 1.754915475845337, 3.468299150466919, 2.106822967529297, 2.435499906539917, 2.634171724319458, 3.331974983215332, 2.659034013748169, 3.059293031692505, 4.22581672668457, 2.9308483600616455, 3.8327887058258057, 2.8388261795043945, 3.056466579437256, 2.944596529006958, 1.8268651962280273, 2.5075442790985107, 3.441206693649292, 2.1750364303588867, 1.4720176458358765, 3.132676839828491, 2.5472898483276367, 3.3893115520477295, 2.717728853225708, 2.3070249557495117, 3.985570192337036, 2.0123376846313477, 3.772664785385132, 3.560053825378418, 1.9865540266036987, 2.120772361755371, 2.443234443664551, 2.2364988327026367, 1.6579618453979492, 3.723220109939575, 3.4236552715301514, 3.1755053997039795, 1.5721409320831299, 2.2237579822540283, 3.416102170944214, 1.9741594791412354, 2.578458309173584, 2.5251646041870117, 1.9926557540893555, 3.14452862739563, 1.6575034856796265, 3.53177547454834, 3.4003782272338867, 2.588759660720825, 2.1737091541290283, 1.8924283981323242, 1.8776159286499023, 2.749133348464966, 1.8023731708526611, 3.385160446166992, 2.13307523727417, 2.439453125, 3.6609203815460205, 2.3811986446380615, 2.3581438064575195, 2.1007676124572754, 2.5161964893341064, 3.7834103107452393, 2.7031948566436768, 3.1746230125427246, 3.1227831840515137, 2.997175931930542, 2.0901479721069336, 1.6673940420150757, 2.9141292572021484, 3.05057692527771, 3.1127965450286865, 3.5370683670043945, 3.984426736831665, 3.3065502643585205, 2.7443530559539795, 3.5337116718292236, 3.16068959236145, 2.766453266143799, 2.515674114227295, 3.142293691635132, 2.2981011867523193, 1.6549395322799683, 3.4446849822998047, 3.16357159614563, 2.852332353591919, 3.2500622272491455, 1.5591259002685547, 2.5709056854248047, 3.602789878845215, 3.37184476852417, 3.161097764968872, 1.6184319257736206, 2.1314337253570557, 2.5599145889282227, 2.901639699935913, 3.292611598968506, 2.7389252185821533, 2.1561150550842285, 3.009305000305176, 2.2993979454040527, 2.924027681350708, 3.231149435043335, 3.345759868621826, 2.6370251178741455, 3.2410783767700195, 3.7612249851226807, 2.598597288131714, 2.3622875213623047, 2.7433886528015137, 2.5141706466674805, 3.283740758895874, 2.61065673828125, 1.595728874206543, 3.6513051986694336, 1.9642614126205444, 3.43497371673584, 3.3993847370147705, 3.8242034912109375, 3.7652158737182617, 4.134398937225342, 3.7925407886505127, 3.0262176990509033, 2.510087728500366, 2.704071521759033, 2.611926555633545, 2.221269369125366, 2.274134635925293, 2.8995068073272705, 3.491337776184082, 2.652982711791992, 2.54618763923645, 1.5868215560913086, 2.285005807876587, 2.1800928115844727, 2.5174131393432617, 2.790087938308716, 2.7214436531066895, 2.45839786529541, 1.729517936706543, 4.06629753112793, 3.1171791553497314, 3.146111488342285, 2.207444429397583, 2.4184534549713135, 1.7176058292388916, 3.117105722427368, 1.6824064254760742, 2.830533266067505, 2.704207420349121, 3.11308217048645, 1.7665215730667114, 2.5794644355773926, 3.263200044631958, 1.7546110153198242, 3.5328292846679688, 2.3430681228637695, 2.5080461502075195, 1.9367423057556152, 3.018784761428833, 2.4476232528686523, 2.5266733169555664, 3.6566402912139893, 3.7210447788238525, 2.651883602142334, 3.375369071960449, 1.9117460250854492, 3.0409367084503174, 2.3242547512054443, 0.27024057507514954, 0.23809586465358734, 0.23191943764686584, 0.2651546597480774, 0.2480444312095642, 0.23875969648361206, 0.272227942943573, 0.23014399409294128, 0.3263665735721588, 0.20326602458953857, 0.23902954161167145, 0.24587787687778473, 0.3048842251300812, 0.2587558329105377, 0.308643639087677, 0.22382119297981262, 0.24692362546920776, 0.268164724111557, 0.26064521074295044, 0.25452515482902527, 0.2796439230442047, 0.2794457674026489, 0.2607076168060303, 0.24515914916992188, 0.1750340461730957, 0.260466605424881, 0.30076053738594055, 0.32038459181785583, 0.26341214776039124, 0.205250546336174, 0.25621744990348816, 0.3051159679889679, 0.31579750776290894, 0.25389206409454346, 0.2497357875108719, 0.2242916375398636, 0.19508811831474304, 0.26575252413749695, 0.27188587188720703, 0.26004859805107117, 0.26860323548316956, 0.27920272946357727, 0.27996909618377686, 0.21311882138252258, 0.2712138295173645, 0.2536519765853882, 0.21441707015037537, 0.20581845939159393, 0.2433551698923111, 0.19737444818019867, 0.2769603729248047, 0.321796715259552, 0.3196996748447418, 0.2531866133213043, 0.21453231573104858, 0.25356563925743103, 0.2725847661495209, 0.21776984632015228, 0.28124216198921204, 0.2507898807525635, 0.262203186750412, 0.22231805324554443, 0.2838985323905945, 0.2865164577960968, 0.22137923538684845, 0.26304957270622253, 0.2913303077220917, 0.21071818470954895, 0.206919327378273, 0.20173795521259308, 0.26008355617523193, 0.29361438751220703, 0.23735281825065613, 0.28896254301071167, 0.2933279871940613, 0.22134339809417725, 0.31591594219207764, 0.21594612300395966, 0.2926245331764221, 0.2557016611099243, 0.20960116386413574, 0.32990482449531555, 0.24107028543949127, 0.23848608136177063, 0.30357107520103455, 0.3341347575187683, 0.18514887988567352, 0.2479354441165924, 0.2876504361629486, 0.26350075006484985, 0.2678621709346771, 0.22854052484035492, 0.3083077073097229, 0.21774554252624512, 0.2178475558757782, 0.23854564130306244, 0.3241232931613922, 0.2774963676929474, 0.2527579963207245, 0.2074885368347168, 0.20219428837299347, 0.26443925499916077, 0.28196361660957336, 0.2672312557697296, 0.23030051589012146, 0.24733954668045044, 0.2789502739906311, 0.24045966565608978, 0.26973047852516174, 0.25355264544487, 0.210166335105896, 0.23697760701179504, 0.23708589375019073, 0.2225152850151062, 0.16819214820861816, 0.25960129499435425, 0.2770354151725769, 0.2308502495288849, 0.3359890580177307, 0.24674265086650848, 0.22009581327438354, 0.3006223142147064, 0.2472643405199051, 0.28524190187454224, 0.26606422662734985, 0.24705155193805695, 0.2613031268119812, 0.2875255048274994, 0.20952208340168, 0.24247749149799347, 0.22413058578968048, 0.2148997038602829, 0.2756538987159729, 0.21889477968215942, 0.2762196958065033, 0.2002454400062561, 0.2635766565799713, 0.2655992805957794, 0.22151900827884674, 0.23742999136447906, 0.19299843907356262, 0.2793954908847809, 0.32118019461631775, 0.2223406583070755, 0.22478832304477692, 0.21406616270542145, 0.29536139965057373, 0.23210403323173523, 0.24665729701519012, 0.28676319122314453, 0.28746023774147034, 0.23572081327438354, 0.2285068780183792, 0.2685416042804718, 0.287117600440979, 0.2252926528453827, 0.21069283783435822, 0.23182670772075653, 0.30416151881217957, 0.22735051810741425, 0.26365041732788086, 0.27548691630363464, 0.2607380151748657, 0.27024078369140625, 0.33012256026268005, 0.25075870752334595, 0.23949824273586273, 0.3185819387435913, 0.23036091029644012, 0.23127394914627075, 0.2745112478733063, 0.2798926532268524, 0.22895751893520355, 0.2380630075931549, 0.30624935030937195, 0.22637593746185303, 0.3079596161842346, 0.3347322642803192, 0.224191814661026, 0.29002252221107483, 0.30120596289634705, 0.19771531224250793, 0.23917147517204285, 0.24095870554447174, 0.2630522549152374, 0.33826541900634766, 0.2269112765789032, 0.25753581523895264, 0.2520259916782379, 0.2738470733165741, 0.31572723388671875, 0.180525541305542, 0.25385263562202454, 0.30867576599121094, 0.301071435213089, 0.2304832637310028, 0.22791965305805206, 0.22725726664066315, 0.2504083812236786, 0.2062584012746811, 0.22711598873138428, 0.21525947749614716, 0.2293040007352829, 0.3377368152141571, 0.2691769301891327, 0.28161823749542236, 0.21648751199245453, 0.2848350405693054, 0.23474186658859253, 0.25641554594039917, 0.2024160474538803, 0.22761671245098114, 0.26959002017974854, 0.22370955348014832, 0.2361254245042801, 0.2035789042711258, 0.2551797032356262, 0.26120617985725403, 0.18878650665283203, 0.2557596266269684, 0.2087446004152298, 0.2333623766899109, 0.23338204622268677, 0.16643592715263367, 0.277281254529953, 0.28435325622558594, 0.26271674036979675, 0.2961879372596741, 0.23045466840267181, 0.2996474504470825, 0.265304833650589, 0.2751762270927429, 0.27350783348083496, 0.3130302429199219, 0.26577499508857727, 0.2492353916168213, 0.231928750872612, 0.2989499568939209, 0.2597896456718445, 0.24554912745952606, 0.23727944493293762, 0.24093009531497955, 0.2927757501602173, 0.29215794801712036, 0.233415886759758, 0.2579262852668762, 0.26900309324264526, 0.23234790563583374, 0.345885694026947, 0.21148617565631866, 0.2462698519229889, 0.30160877108573914, 0.2632361650466919, 0.2596627473831177, 0.3029467761516571, 0.22212760150432587, 0.2670252025127411, 0.27112898230552673, 0.34691321849823, 0.24684281647205353, 0.25987154245376587, 0.27573680877685547, 0.2534765303134918, 0.20883022248744965, 0.23264048993587494, 0.27513429522514343, 0.231784850358963, 0.3658675253391266, 0.21823954582214355, 0.2506198585033417, 0.24069319665431976, 0.28713786602020264, 0.2550061047077179, 0.2746468782424927, 0.25012314319610596, 0.25299304723739624, 0.28033286333084106, 0.27699223160743713, 0.25586509704589844, 0.19310128688812256, 0.3166062533855438, 0.19007277488708496, 0.28107327222824097, 0.2845074236392975, 0.23876182734966278, 0.29000774025917053, 0.25136423110961914, 0.2006455957889557, 0.28581327199935913, 0.1889243721961975, 0.3415137827396393, 0.1993912011384964, 0.26642176508903503, 0.21095550060272217, 0.2842213809490204, 0.22676707804203033, 0.2706276774406433, 0.24965110421180725, 0.27267882227897644, 0.2346038818359375, 4.507027626037598, 3.918781042098999, 2.914738893508911, 3.202333927154541, 2.7753896713256836, 2.841762065887451, 2.201953411102295, 3.641312837600708, 4.119603157043457, 3.703667163848877, 3.8385255336761475, 3.0028645992279053, 2.9312961101531982, 2.4062743186950684, 3.215094804763794, 3.7050387859344482, 2.821779727935791, 2.188537359237671, 3.1426448822021484, 3.8114254474639893, 4.94429349899292, 2.551985502243042, 3.384587049484253, 4.583690166473389, 3.138648271560669, 2.346933603286743, 3.911342144012451, 3.2586631774902344, 2.6152617931365967, 3.037135362625122, 3.6141650676727295, 3.6572844982147217, 4.204323768615723, 3.250627279281616, 3.1818389892578125, 4.254909515380859, 4.715550422668457, 2.5287528038024902, 3.0090973377227783, 4.079009532928467, 2.8179614543914795, 3.5147366523742676, 4.037967205047607, 4.037230968475342, 2.9748871326446533, 3.010643243789673, 3.207869291305542, 2.3907625675201416, 2.034996509552002, 2.901028871536255, 2.9261882305145264, 2.3698790073394775, 3.253373146057129, 3.895958423614502, 3.210088014602661, 3.309725761413574, 2.8538594245910645, 3.8433494567871094, 2.8758373260498047, 3.56500244140625, 3.434574604034424, 3.4330620765686035, 2.6163859367370605, 3.7416844367980957, 3.8917794227600098, 3.058218002319336, 2.6062588691711426, 3.201420307159424, 2.7017810344696045, 2.7459006309509277, 2.218752861022949, 2.609165668487549, 2.7629175186157227, 4.328603267669678, 3.3277828693389893, 4.063725471496582, 3.438133716583252, 3.613354444503784, 4.268517971038818, 3.647373676300049, 3.2512316703796387, 4.150062561035156, 4.739521503448486, 5.393347263336182, 4.208589553833008, 3.3360390663146973, 2.7570106983184814, 3.134650468826294, 3.1531670093536377, 4.063677787780762, 4.053239822387695, 2.937969207763672, 3.1371994018554688, 4.2477006912231445, 3.656588554382324, 4.120642185211182, 3.984056234359741, 3.889120101928711, 3.8475537300109863, 3.797294855117798, 3.2665791511535645, 2.8138649463653564, 2.628615617752075, 3.4304089546203613, 3.256641149520874, 3.216320753097534, 3.4005630016326904, 2.266714334487915, 3.2192177772521973, 4.1189374923706055, 3.61894154548645, 2.9635417461395264, 2.5480844974517822, 4.149867057800293, 3.910329818725586, 3.634669780731201, 3.9528520107269287, 3.5612292289733887, 3.3875889778137207, 2.521961212158203, 3.361279249191284, 3.908606767654419, 3.2923507690429688, 2.3502442836761475, 4.722379207611084, 4.457367420196533, 2.048637866973877, 4.758358478546143, 3.20646595954895, 4.387399673461914, 3.9042539596557617, 2.635087251663208, 4.5506272315979, 5.593237400054932, 3.244929075241089, 3.6276485919952393, 3.190490961074829, 3.8753437995910645, 3.5049350261688232, 4.690029144287109, 3.301483154296875, 3.8915963172912598, 4.587679862976074, 3.692924976348877, 2.971417188644409, 3.371251344680786, 3.5246734619140625, 4.601046085357666, 5.112168312072754, 2.7038073539733887, 3.912036657333374, 2.072077989578247, 3.6513946056365967, 4.511146068572998, 3.133073091506958, 2.8855462074279785, 4.955641269683838, 4.399122714996338, 5.163489818572998, 4.894436359405518, 3.0489087104797363, 3.708409547805786, 2.945737838745117, 2.5506880283355713, 4.0626935958862305, 2.5585198402404785, 3.2653093338012695, 2.929424285888672, 2.6040782928466797, 3.821707010269165, 2.926253080368042, 3.1085193157196045, 3.596752166748047, 4.008976459503174, 3.0994763374328613, 3.360496997833252, 3.7043285369873047, 4.9530768394470215, 3.7490909099578857, 3.6257927417755127, 3.5433928966522217, 4.1042304039001465, 3.8767411708831787, 4.443077087402344, 4.589568614959717, 4.472870826721191, 3.67710018157959, 3.801750659942627, 2.3388750553131104, 4.6587347984313965, 2.6474413871765137, 3.9949703216552734, 2.924851655960083, 4.150285720825195, 4.17529296875, 4.191131114959717, 3.499232769012451, 2.8081212043762207, 3.0881404876708984, 3.5791003704071045, 5.129666805267334, 2.552391529083252, 2.8724124431610107, 4.312835693359375, 3.1208202838897705, 4.2210164070129395, 2.6407904624938965, 3.9889800548553467, 3.533783435821533, 3.795748710632324, 2.974821090698242, 2.2624313831329346, 2.9048919677734375, 2.759173631668091, 3.431447982788086, 2.4966025352478027, 3.204610824584961, 4.433395862579346, 3.7650468349456787, 2.199624538421631, 5.186233997344971, 4.376900672912598, 2.1142795085906982, 3.006627321243286, 2.4709765911102295, 2.6075682640075684, 2.985426664352417, 5.089379787445068, 2.549683094024658, 4.6412577629089355, 4.663387298583984, 4.956249237060547, 3.321148633956909, 2.4273269176483154, 4.663785934448242, 3.212430238723755, 2.532268762588501, 4.574440002441406, 2.408639430999756, 4.302230358123779, 4.453439712524414, 2.3450841903686523, 4.229274749755859, 3.2329013347625732, 2.319291830062866, 3.15966534614563, 3.207615852355957, 2.558314323425293, 4.602332592010498, 2.091729164123535, 3.167712450027466, 5.2514495849609375, 4.706702709197998, 3.789219379425049, 3.587836503982544, 3.8018879890441895, 2.451113224029541, 4.44525671005249, 3.1838886737823486, 2.973952531814575, 4.0709004402160645, 2.5689311027526855, 2.1507315635681152, 2.8136982917785645, 3.5770907402038574, 3.2666501998901367, 2.8878800868988037, 4.668074131011963, 2.3816704750061035, 3.2081358432769775, 3.403550386428833, 2.9373486042022705, 3.496150493621826, 3.5219902992248535, 3.3108489513397217, 4.299226760864258, 4.800005912780762, 3.719493865966797, 3.385409355163574, 3.4022445678710938, 3.5613579750061035, 2.5327072143554688, 3.820582389831543, 3.048737049102783, 3.727586507797241, 3.598544120788574, 4.804079532623291, 3.2947709560394287, 2.035583257675171, 3.0443084239959717, 2.22623610496521, 3.5629069805145264, 2.5319230556488037, 4.175597667694092, 4.923868179321289, 3.055162191390991, 2.2714898586273193, 4.850170135498047, 3.17080020904541, 3.570439577102661, 215.56614685058594, 232.6860809326172, 102.46925354003906, 401.2746276855469, 870.43310546875, 69.0041732788086, 224.48733520507812, 83.03492736816406, 371.421875, 193.4014434814453, 424.8626708984375, 236.62075805664062, 538.9922485351562, 206.93826293945312, 336.30084228515625, 178.8201904296875, 325.115966796875, 265.6006164550781, 235.84881591796875, 420.0094299316406, 185.17727661132812, 258.2737121582031, 638.5863037109375, 289.4755859375, 125.8811264038086, 336.92095947265625, 126.95184326171875, 80.528076171875, 191.1529083251953, 213.70083618164062, 75.442138671875, 209.72039794921875, 76.04638671875, 56.80835723876953, 165.8905029296875, 448.6964111328125, 374.7648010253906, 235.7596435546875, 50.85757827758789, 232.89881896972656, 259.08642578125, 371.4193420410156, 74.8687744140625, 178.3065185546875, 264.59539794921875, 84.61483001708984, 170.96449279785156, 566.1787109375, 124.31161499023438, 232.66847229003906, 251.21316528320312, 256.29638671875, 288.5770263671875, 338.57086181640625, 215.6005401611328, 351.0257873535156, 267.3260803222656, 492.2933349609375, 229.28933715820312, 364.98175048828125, 153.30169677734375, 663.6904296875, 304.2769775390625, 388.2174072265625, 79.2425537109375, 275.9916687011719, 130.20411682128906, 207.5927734375, 406.8629455566406, 92.83807373046875, 160.39024353027344, 92.70216369628906, 464.4439697265625, 69.66728973388672, 162.82923889160156, 198.7323760986328, 107.87110900878906, 161.2449493408203, 53.5240478515625, 124.30560302734375, 454.203125, 306.7015075683594, 205.5648193359375, 126.0693359375, 116.66902160644531, 187.007568359375, 181.7807159423828, 200.3299560546875, 110.67052459716797, 198.91270446777344, 56.45572280883789, 170.95968627929688, 146.6782989501953, 459.5689697265625, 281.7142333984375, 372.61431884765625, 197.87557983398438, 338.3351745605469, 241.03038024902344, 197.88980102539062, 74.35649871826172, 248.49444580078125, 231.47080993652344, 264.74530029296875, 262.2353515625, 211.93983459472656, 93.39259338378906, 398.61761474609375, 66.9532470703125, 238.8692169189453, 344.222412109375, 411.7994384765625, 128.291748046875, 292.4944152832031, 186.24037170410156, 120.41903686523438, 188.75059509277344, 165.4152069091797, 151.9806671142578, 415.337646484375, 315.4627685546875, 265.603515625, 613.424560546875, 222.17543029785156, 255.8216552734375, 399.5078125, 71.5440673828125, 363.2411193847656, 346.4398498535156, 418.5361328125, 441.9234924316406, 128.6009521484375, 62.21966552734375, 134.97572326660156, 280.0284423828125, 116.89111328125, 222.36380004882812, 212.896240234375, 331.4229736328125, 365.2213134765625, 65.41790771484375, 467.0035095214844, 570.5016479492188, 465.037841796875, 354.7833557128906, 137.57650756835938, 260.05810546875, 178.3103485107422, 477.54351806640625, 499.4413146972656, 527.644287109375, 248.5657958984375, 207.5902862548828, 258.0763244628906, 258.04010009765625, 133.04066467285156, 426.322021484375, 242.8782958984375, 274.0732116699219, 182.97756958007812, 306.2088623046875, 131.59999084472656, 281.7160949707031, 175.80186462402344, 190.20957946777344, 71.4044189453125, 142.743896484375, 101.39418029785156, 323.58074951171875, 261.346435546875, 431.1241760253906, 352.8916015625, 381.1124572753906, 123.1014633178711, 57.5283203125, 96.50826263427734, 458.6935729980469, 345.31549072265625, 412.1955261230469, 265.3236999511719, 197.86390686035156, 297.34039306640625, 309.0820617675781, 255.31175231933594, 43.016483306884766, 152.904052734375, 112.35478973388672, 363.0027770996094, 56.11985778808594, 394.0106201171875, 72.60560607910156, 230.390380859375, 611.119140625, 231.84625244140625, 295.9563903808594, 200.92544555664062, 189.0882568359375, 184.8968505859375, 186.05918884277344, 215.24159240722656, 351.9864807128906, 255.4868927001953, 220.7530059814453, 434.0052185058594, 265.1252136230469, 313.5456848144531, 133.38966369628906, 336.6961364746094, 100.85796356201172, 306.5622863769531, 141.37620544433594, 94.7537841796875, 503.4193115234375, 333.76983642578125, 115.58109283447266, 173.88796997070312, 171.44058227539062, 288.0168151855469, 502.2052917480469, 341.4286193847656, 525.3134155273438, 414.9669494628906, 381.7003479003906, 433.9427185058594, 238.6541748046875, 156.21583557128906, 107.35798645019531, 196.8103485107422, 316.8553161621094, 252.5077362060547, 187.73733520507812, 346.3250427246094, 314.0314636230469, 532.4917602539062, 423.1794738769531, 167.89405822753906, 65.01737976074219, 224.54714965820312, 201.0810089111328, 715.1234741210938, 149.98367309570312, 196.9540252685547, 218.4580841064453, 243.9862823486328, 402.7149963378906, 768.5836791992188, 322.5975341796875, 256.8249816894531, 399.90045166015625, 122.37853240966797, 326.765380859375, 231.01573181152344, 379.35296630859375, 275.4669189453125, 63.970115661621094, 710.8171997070312, 347.0689392089844, 373.2359924316406, 128.15162658691406, 427.413818359375, 304.5818786621094, 347.0321350097656, 53.0155029296875, 443.592529296875, 113.568359375, 547.6713256835938, 168.36358642578125, 330.18487548828125, 103.91773986816406, 460.423583984375, 47.9794921875, 452.89007568359375, 170.6960906982422, 177.339111328125, 481.323974609375, 208.6646270751953, 99.28271484375, 240.85296630859375, 272.86248779296875, 361.5652770996094, 136.3759765625, 82.7088623046875, 449.0611572265625, 412.1877136230469, 292.1798095703125, 435.990966796875, 197.376708984375, 196.8450927734375, 225.46435546875, 444.35015869140625, 184.7117919921875, 303.1136474609375, 686.5330200195312, 235.68663024902344, 251.6239013671875, 286.84796142578125, 379.2711486816406, 203.18722534179688, 342.72039794921875, 283.2891845703125, 2.40057635307312, 3.2383644580841064, 3.6307554244995117, 3.3838720321655273, 2.463515520095825, 1.8153190612792969, 2.4903688430786133, 2.414564371109009, 2.9793925285339355, 2.4665746688842773, 1.808045744895935, 3.9156315326690674, 1.7564517259597778, 3.928461790084839, 1.9943140745162964, 3.4406003952026367, 2.1821467876434326, 4.247727394104004, 2.5626847743988037, 1.6884745359420776, 2.2242588996887207, 2.202511787414551, 2.0858774185180664, 2.69309139251709, 2.375002145767212, 2.1562891006469727, 3.2743377685546875, 3.920250177383423, 3.8335506916046143, 2.145078182220459, 3.526604652404785, 1.5133637189865112, 3.174410343170166, 3.1076784133911133, 2.9030568599700928, 4.041142463684082, 1.9277126789093018, 1.4219274520874023, 2.437924861907959, 2.2117128372192383, 2.3381402492523193, 3.2323429584503174, 1.2047611474990845, 1.3702694177627563, 4.040668964385986, 3.6730542182922363, 1.918307900428772, 1.7014745473861694, 4.066102027893066, 2.7027177810668945, 3.1052751541137695, 3.4417126178741455, 3.3457226753234863, 2.837864875793457, 1.5563081502914429, 3.09401798248291, 2.3801071643829346, 2.2793397903442383, 4.027999401092529, 3.5183379650115967, 3.459702968597412, 3.2896173000335693, 3.0158488750457764, 3.5968270301818848, 2.257870674133301, 2.032304286956787, 1.4542707204818726, 2.3141472339630127, 1.8047937154769897, 3.1747350692749023, 3.131653308868408, 2.928394317626953, 1.8072607517242432, 3.392352819442749, 1.3732526302337646, 2.6696157455444336, 3.078178882598877, 2.5004208087921143, 1.695245623588562, 3.012195348739624, 3.272580146789551, 1.8846782445907593, 2.0587689876556396, 2.8347463607788086, 2.7811005115509033, 2.8025786876678467, 3.558589458465576, 1.9022060632705688, 2.892047166824341, 1.3278777599334717, 2.85793399810791, 2.888139009475708, 1.684657096862793, 3.419092893600464, 1.5354135036468506, 2.3449597358703613, 2.401127815246582, 3.3525960445404053, 3.0489418506622314, 2.9458837509155273, 2.9141910076141357, 3.2448675632476807, 2.8544561862945557, 2.901658296585083, 1.7953624725341797, 2.3689002990722656, 2.398348093032837, 3.206177234649658, 3.124955415725708, 3.131749153137207, 2.094386100769043, 3.070265531539917, 3.074927568435669, 1.683985710144043, 3.368391752243042, 3.420874834060669, 1.8197858333587646, 3.103585720062256, 2.857281446456909, 3.5019543170928955, 2.5379021167755127, 3.253394603729248, 2.606167793273926, 1.9077614545822144, 3.2744381427764893, 2.5328052043914795, 2.1156463623046875, 2.6138460636138916, 3.1158549785614014, 4.132943153381348, 2.5989019870758057, 3.02227783203125, 2.109687089920044, 3.240614175796509, 3.3539745807647705, 3.8359978199005127, 2.255740165710449, 1.859985113143921, 3.245526075363159, 1.584999918937683, 1.8522902727127075, 2.0736780166625977, 3.1125078201293945, 3.16161847114563, 2.975309371948242, 2.455122947692871, 1.8540525436401367, 4.174983024597168, 2.119649648666382, 2.8231048583984375, 3.060922861099243, 3.5889785289764404, 2.7476184368133545, 3.196765899658203, 1.7542874813079834, 2.769606828689575, 4.234537124633789, 2.394454002380371, 2.668179988861084, 3.2348875999450684, 2.5589303970336914, 2.4695959091186523, 1.7605504989624023, 3.292051315307617, 2.452267646789551, 2.1676242351531982, 2.1996710300445557, 2.639085054397583, 2.39421010017395, 2.4129397869110107, 2.6508281230926514, 3.0794341564178467, 2.938246965408325, 3.1807947158813477, 2.5737624168395996, 3.1107192039489746, 2.5750133991241455, 1.8700628280639648, 2.038395404815674, 3.3425657749176025, 2.941542863845825, 2.026470184326172, 2.3349428176879883, 2.0757036209106445, 3.862940788269043, 2.5287983417510986, 2.894270658493042, 2.461113691329956, 3.1628923416137695, 3.6629838943481445, 2.9477736949920654, 4.074264049530029, 1.6558053493499756, 2.8201382160186768, 2.521568536758423, 4.232004165649414, 3.689213752746582, 2.5670695304870605, 2.2172954082489014, 3.338547945022583, 3.8049333095550537, 2.0829858779907227, 1.9568243026733398, 2.83396053314209, 1.866158127784729, 1.1908330917358398, 3.0843288898468018, 2.002971649169922, 2.697445869445801, 3.048016309738159, 2.125699043273926, 1.8306504487991333, 2.6109650135040283, 3.01578688621521, 2.311521053314209, 2.6694881916046143, 3.842108964920044, 3.3779592514038086, 1.7137879133224487, 2.4042842388153076, 2.238966941833496, 2.8693695068359375, 2.18966007232666, 2.9402096271514893, 3.9484307765960693, 1.8768975734710693, 2.3575923442840576, 1.9182747602462769, 2.4590377807617188, 2.9734649658203125, 2.325514793395996, 3.422044277191162, 2.731738328933716, 3.593632698059082, 2.1272940635681152, 3.072514533996582, 2.7034032344818115, 2.8664028644561768, 3.1143829822540283, 2.7514891624450684, 1.7244672775268555, 3.1089794635772705, 2.059889793395996, 1.962044596672058, 2.2985849380493164, 2.3826651573181152, 2.7717278003692627, 3.459681510925293, 1.368003487586975, 2.97048282623291, 2.5401387214660645, 1.2898516654968262, 2.6466124057769775, 2.4689455032348633, 1.978087306022644, 3.3454349040985107, 3.34978985786438, 2.042342185974121, 2.681353807449341, 1.854400873184204, 3.75541090965271, 1.3952680826187134, 2.6686348915100098, 2.7482712268829346, 3.3825042247772217, 3.3595244884490967, 2.60733962059021, 2.726083517074585, 2.4080705642700195, 2.446038246154785, 2.4822590351104736, 2.1138925552368164, 4.430450439453125, 3.247385263442993, 2.40341854095459, 2.555295467376709, 1.2756054401397705, 2.5064616203308105, 2.3953943252563477, 2.465104103088379, 2.8225810527801514, 1.7458932399749756, 2.623615026473999, 3.669276714324951, 1.5934667587280273, 3.778323173522949, 3.693953275680542, 2.9531877040863037, 2.762101888656616, 2.592235565185547, 2.1692326068878174, 2.473238706588745, 3.3620262145996094, 2.449965476989746, 2.012820243835449, 1.9737272262573242, 2.997676134109497, 1.5222686529159546, 2.580989122390747, 2.450126886367798, 0.24410733580589294, 0.21056579053401947, 0.24605119228363037, 0.21656373143196106, 0.25952690839767456, 0.2711693048477173, 0.2199956774711609, 0.2769192159175873, 0.27422666549682617, 0.29015615582466125, 0.21404457092285156, 0.22193068265914917, 0.2797771096229553, 0.2624245285987854, 0.23958277702331543, 0.24617794156074524, 0.21241946518421173, 0.2514580488204956, 0.32297441363334656, 0.2939381003379822, 0.23336949944496155, 0.26978591084480286, 0.24504965543746948, 0.231386199593544, 0.22489012777805328, 0.22451448440551758, 0.25213348865509033, 0.2428748607635498, 0.27535587549209595, 0.1977381408214569, 0.25223591923713684, 0.22590140998363495, 0.23529304563999176, 0.2535064220428467, 0.30276572704315186, 0.2505435049533844, 0.22093327343463898, 0.1824996918439865, 0.28497830033302307, 0.2878066599369049, 0.31884709000587463, 0.276034951210022, 0.2561895549297333, 0.21984267234802246, 0.2538718283176422, 0.21528123319149017, 0.2535543441772461, 0.28600624203681946, 0.2758808135986328, 0.20368728041648865, 0.2648651897907257, 0.24811522662639618, 0.26884716749191284, 0.30093029141426086, 0.2544577717781067, 0.2456800788640976, 0.2857339680194855, 0.26262205839157104, 0.21367919445037842, 0.33109015226364136, 0.242483451962471, 0.2559523284435272, 0.2541545331478119, 0.2467164546251297, 0.2349410057067871, 0.24717307090759277, 0.34403762221336365, 0.2535359859466553, 0.31187644600868225, 0.27286896109580994, 0.2576926648616791, 0.24144987761974335, 0.2858392298221588, 0.22716474533081055, 0.3084971308708191, 0.23225738108158112, 0.28157860040664673, 0.26374882459640503, 0.27782636880874634, 0.2603798508644104, 0.21355962753295898, 0.30552470684051514, 0.2996741831302643, 0.25462737679481506, 0.2931431233882904, 0.3101164698600769, 0.3470308482646942, 0.3256899118423462, 0.25455641746520996, 0.2421659678220749, 0.33237898349761963, 0.28099092841148376, 0.23835448920726776, 0.24765822291374207, 0.3009558320045471, 0.24826788902282715, 0.25536230206489563, 0.18305736780166626, 0.24305324256420135, 0.33660101890563965, 0.24897350370883942, 0.281527578830719, 0.24261628091335297, 0.26896992325782776, 0.2844902575016022, 0.2192680686712265, 0.2897741198539734, 0.24540476500988007, 0.2568548917770386, 0.23818694055080414, 0.268019437789917, 0.2344411462545395, 0.258716344833374, 0.2626440227031708, 0.20280657708644867, 0.24391984939575195, 0.22714169323444366, 0.27649614214897156, 0.3178432583808899, 0.2005542367696762, 0.28584399819374084, 0.219989612698555, 0.254416823387146, 0.2623238265514374, 0.26319506764411926, 0.2811140716075897, 0.2746710479259491, 0.25057461857795715, 0.2682250142097473, 0.2622543275356293, 0.2157781571149826, 0.23282909393310547, 0.21826434135437012, 0.285898894071579, 0.2904687225818634, 0.29814690351486206, 0.21532946825027466, 0.24875186383724213, 0.2731330394744873, 0.3206300735473633, 0.2490806132555008, 0.25514906644821167, 0.250467985868454, 0.26862069964408875, 0.18869423866271973, 0.2688327431678772, 0.32413649559020996, 0.22310781478881836, 0.2197120636701584, 0.20476989448070526, 0.25625547766685486, 0.22659987211227417, 0.24759157001972198, 0.3296951353549957, 0.2730712890625, 0.24773968756198883, 0.275203138589859, 0.21522197127342224, 0.23068416118621826, 0.2473309338092804, 0.22978805005550385, 0.22457286715507507, 0.24035944044589996, 0.2655368447303772, 0.29868146777153015, 0.21872515976428986, 0.24665039777755737, 0.23247146606445312, 0.24123038351535797, 0.2674230635166168, 0.2230260819196701, 0.2676665186882019, 0.2668980062007904, 0.3398587703704834, 0.28519758582115173, 0.30104202032089233, 0.27369245886802673, 0.26046887040138245, 0.28913116455078125, 0.3452175557613373, 0.27056899666786194, 0.24293263256549835, 0.228971928358078, 0.2621825635433197, 0.281711220741272, 0.2188325822353363, 0.3210100531578064, 0.28431254625320435, 0.2615320086479187, 0.25731322169303894, 0.21615725755691528, 0.2742724120616913, 0.26156938076019287, 0.22494356334209442, 0.27628809213638306, 0.174265056848526, 0.24252437055110931, 0.30681300163269043, 0.27120310068130493, 0.2616634964942932, 0.2545180320739746, 0.28387874364852905, 0.2601686120033264, 0.2588613033294678, 0.2937999963760376, 0.26973360776901245, 0.3087829053401947, 0.30861911177635193, 0.17650435864925385, 0.20464900135993958, 0.2510274052619934, 0.2401173859834671, 0.22432701289653778, 0.2099788933992386, 0.29571932554244995, 0.24746817350387573, 0.26819342374801636, 0.2465302050113678, 0.28626909852027893, 0.25382524728775024, 0.28622379899024963, 0.26755961775779724, 0.31134137511253357, 0.24903559684753418, 0.21792522072792053, 0.27888891100883484, 0.20456740260124207, 0.23164057731628418, 0.27101919054985046, 0.2154703438282013, 0.31228137016296387, 0.27312731742858887, 0.2952204942703247, 0.27584215998649597, 0.2704574167728424, 0.1883595585823059, 0.2733961343765259, 0.23185205459594727, 0.18093974888324738, 0.2728423774242401, 0.20511861145496368, 0.25831085443496704, 0.2658703625202179, 0.22949044406414032, 0.33394357562065125, 0.2617914080619812, 0.26672908663749695, 0.18882085382938385, 0.24289332330226898, 0.2061043083667755, 0.2496669739484787, 0.29050302505493164, 0.2826715409755707, 0.20283660292625427, 0.3211354613304138, 0.2899724245071411, 0.2441471964120865, 0.2882575988769531, 0.2835468351840973, 0.24626289308071136, 0.2954833209514618, 0.2583064138889313, 0.3708707392215729, 0.24065189063549042, 0.23091888427734375, 0.250814288854599, 0.19285368919372559, 0.24859336018562317, 0.2700885534286499, 0.22183755040168762, 0.19627612829208374, 0.25862956047058105, 0.26800060272216797, 0.27153730392456055, 0.30619388818740845, 0.22339625656604767, 0.27225571870803833, 0.3215542435646057, 0.23844851553440094, 0.23078493773937225, 0.24507442116737366, 0.2577228546142578, 0.26062172651290894, 0.2712670862674713, 0.2338145524263382, 0.3162989318370819, 0.37331435084342957, 0.25346705317497253, 0.31171438097953796, 0.2685335576534271, 0.26210975646972656, 0.2751893103122711, 0.23431213200092316, 0.25513431429862976, 0.24077336490154266, 0.22928138077259064, 0.3242031931877136, 0.1929105520248413, 0.30124130845069885, 0.28184911608695984, 3.292649984359741, 2.3067166805267334, 2.8714535236358643, 2.2515041828155518, 2.6860997676849365, 2.720404863357544, 2.367905855178833, 2.4959328174591064, 3.0822482109069824, 4.379387378692627, 2.662815570831299, 4.362430095672607, 2.8533883094787598, 2.883976936340332, 3.424838066101074, 3.90038800239563, 2.333435535430908, 3.671316146850586, 3.137516736984253, 2.9725921154022217, 3.194645881652832, 3.316415548324585, 3.540098190307617, 3.037567615509033, 4.481905460357666, 2.8548309803009033, 3.376819372177124, 4.536618709564209, 2.1860501766204834, 3.5655224323272705, 3.5200750827789307, 2.6525325775146484, 3.394228935241699, 4.433944225311279, 3.2002861499786377, 3.8425092697143555, 2.9346065521240234, 4.261122226715088, 3.2847652435302734, 4.485823154449463, 1.935785174369812, 3.1684353351593018, 4.053464889526367, 2.995593309402466, 2.5623719692230225, 3.4566738605499268, 3.234522581100464, 3.5836105346679688, 3.1076595783233643, 2.901231050491333, 2.8971333503723145, 4.2977399826049805, 5.680997371673584, 2.6151528358459473, 3.6547768115997314, 2.3158764839172363, 4.470735549926758, 3.365804672241211, 3.716623067855835, 4.252109050750732, 4.04067325592041, 2.2833776473999023, 2.8485374450683594, 3.339404821395874, 3.6737866401672363, 2.7845540046691895, 2.655348539352417, 3.114508867263794, 3.313502788543701, 2.8771793842315674, 2.3707759380340576, 4.353825569152832, 1.871399164199829, 2.621549129486084, 3.6076934337615967, 4.208770275115967, 2.6584911346435547, 4.1361494064331055, 3.84549880027771, 3.4619534015655518, 3.21471905708313, 3.432631731033325, 2.5414562225341797, 2.8489227294921875, 3.3213963508605957, 2.954897403717041, 2.3906803131103516, 2.6590142250061035, 3.0063445568084717, 2.8657143115997314, 3.1036102771759033, 4.2604851722717285, 3.2836861610412598, 4.594463348388672, 3.1060473918914795, 3.446744203567505, 3.6429641246795654, 3.6487033367156982, 2.872969388961792, 3.200138568878174, 3.4509084224700928, 4.465177536010742, 3.7420356273651123, 2.503262996673584, 3.2340614795684814, 2.556143045425415, 3.5687572956085205, 3.686225175857544, 4.42987060546875, 3.615684986114502, 2.6572539806365967, 4.01200532913208, 3.318040132522583, 4.780522346496582, 4.214120864868164, 3.5773801803588867, 2.202178716659546, 3.143465280532837, 3.9032063484191895, 2.7043633460998535, 3.826953649520874, 3.0691375732421875, 2.6452765464782715, 4.669864177703857, 2.4760653972625732, 3.0407402515411377, 3.5533647537231445, 5.2828192710876465, 2.6620571613311768, 4.232964515686035, 2.9667248725891113, 2.6724343299865723, 5.035858154296875, 2.8893980979919434, 2.830601692199707, 2.7466704845428467, 2.585723876953125, 2.575960636138916, 2.9835140705108643, 3.1297624111175537, 4.235393047332764, 3.052429676055908, 2.011953115463257, 2.3961801528930664, 2.708652973175049, 2.6647655963897705, 3.1765434741973877, 4.796329021453857, 3.6654293537139893, 2.208082437515259, 3.2814700603485107, 4.611140727996826, 4.258534908294678, 2.5632033348083496, 2.4957263469696045, 3.301333427429199, 4.369774341583252, 3.5671451091766357, 3.5389344692230225, 2.589282751083374, 3.5993282794952393, 2.98382830619812, 4.059662818908691, 2.3321073055267334, 4.244699478149414, 4.224051475524902, 3.2994678020477295, 4.405274391174316, 2.535560131072998, 3.255450963973999, 2.393176555633545, 3.017218828201294, 3.133307695388794, 2.822526693344116, 4.767062664031982, 3.0025699138641357, 3.533029317855835, 4.256275653839111, 2.075932025909424, 4.616909027099609, 4.153770923614502, 3.05869460105896, 3.4488906860351562, 2.6561546325683594, 4.371061325073242, 2.5572829246520996, 3.047459840774536, 4.225520133972168, 3.032182455062866, 3.1153512001037598, 2.9184234142303467, 2.289384365081787, 3.427170991897583, 2.9190478324890137, 3.881591796875, 3.8210930824279785, 2.4320504665374756, 3.7746763229370117, 2.807283878326416, 4.012021541595459, 2.9712910652160645, 2.8646984100341797, 3.919523239135742, 3.9482667446136475, 2.6190624237060547, 2.6844615936279297, 4.102200984954834, 2.774500608444214, 3.010943651199341, 5.370748996734619, 3.616741895675659, 2.870023727416992, 2.3947525024414062, 2.307995319366455, 2.4502127170562744, 2.486464262008667, 3.1041786670684814, 3.9022610187530518, 4.057132244110107, 3.0856258869171143, 2.939692258834839, 3.674747943878174, 2.9847447872161865, 4.958075523376465, 2.653625965118408, 3.5750792026519775, 3.0890660285949707, 4.0151872634887695, 5.120937347412109, 3.897484064102173, 3.385272741317749, 2.7268078327178955, 3.3586361408233643, 2.5950992107391357, 3.2546207904815674, 2.6715424060821533, 2.614621639251709, 4.068739414215088, 3.6163170337677, 2.2517759799957275, 3.7117490768432617, 3.113398790359497, 3.944728374481201, 6.197719573974609, 2.7365498542785645, 3.338198661804199, 2.796910524368286, 2.8503899574279785, 3.2512714862823486, 3.039128303527832, 3.6009318828582764, 1.6410415172576904, 3.8877251148223877, 4.043544769287109, 2.6075334548950195, 3.0940215587615967, 3.6776952743530273, 3.0344040393829346, 2.6645026206970215, 3.690321683883667, 2.6458210945129395, 2.664104461669922, 2.900128126144409, 3.728541374206543, 4.514585494995117, 2.1062424182891846, 3.252830982208252, 2.721863269805908, 3.5044732093811035, 5.386728286743164, 3.2885067462921143, 2.6781857013702393, 5.301989555358887, 4.079440593719482, 2.725977659225464, 2.7684390544891357, 2.6780037879943848, 2.0784337520599365, 3.165494918823242, 4.062658309936523, 4.312286376953125, 2.3871288299560547, 2.5572609901428223, 2.6690690517425537, 3.0744545459747314, 3.0674407482147217, 2.926562547683716, 2.9283251762390137, 3.610154390335083, 2.418031930923462, 2.412127733230591, 3.8107898235321045, 4.149682998657227, 2.800217866897583, 4.461535453796387, 4.032828330993652, 3.2837846279144287, 4.452205657958984, 4.921331882476807, 4.404439926147461, 494.119140625, 474.7935485839844, 130.803466796875, 198.2411651611328, 351.67218017578125, 398.2853088378906, 182.80874633789062, 275.4472351074219, 79.7845458984375, 71.083740234375, 287.622802734375, 349.76727294921875, 142.44679260253906, 318.64813232421875, 129.56085205078125, 57.52004623413086, 468.9924011230469, 283.6531982421875, 603.70654296875, 89.99571990966797, 622.739990234375, 68.6646957397461, 67.2693862915039, 388.634765625, 249.41156005859375, 530.1685791015625, 63.02125930786133, 541.863525390625, 221.5579833984375, 224.07579040527344, 285.8565979003906, 123.66020965576172, 321.3216552734375, 272.90081787109375, 409.5213928222656, 431.498046875, 127.49659729003906, 210.9680938720703, 239.3013153076172, 218.1942596435547, 126.94197082519531, 109.3515625, 276.4671325683594, 558.6143188476562, 385.86773681640625, 43.65127182006836, 647.103515625, 118.71437072753906, 127.94117736816406, 525.45947265625, 288.2499084472656, 234.53526306152344, 86.95294952392578, 399.408935546875, 272.5765380859375, 438.1925964355469, 182.89561462402344, 389.1981506347656, 147.74163818359375, 106.91950988769531, 306.2774658203125, 237.315185546875, 370.6031188964844, 441.0481872558594, 309.9376525878906, 160.1571807861328, 220.4085693359375, 387.3609924316406, 180.7010955810547, 471.71624755859375, 198.4918975830078, 483.98492431640625, 114.8759765625, 365.9967041015625, 129.16754150390625, 320.8624572753906, 297.47607421875, 65.15190887451172, 121.30913543701172, 89.03054809570312, 306.2132263183594, 573.2484741210938, 154.32150268554688, 445.1394958496094, 92.0549087524414, 168.9352264404297, 704.2584228515625, 248.81182861328125, 98.56987762451172, 192.2987060546875, 430.0963134765625, 103.09868621826172, 156.3588104248047, 205.75804138183594, 93.25384521484375, 356.4781799316406, 176.5587921142578, 462.1063537597656, 278.8260498046875, 248.9213409423828, 676.1170043945312, 274.9642333984375, 69.66354370117188, 679.2282104492188, 417.0116271972656, 414.6759338378906, 672.3538818359375, 53.67333984375, 226.40890502929688, 470.971435546875, 250.27259826660156, 74.92962646484375, 327.8160095214844, 88.83938598632812, 282.83123779296875, 630.6188354492188, 153.385009765625, 217.71592712402344, 237.28448486328125, 266.8812561035156, 331.350341796875, 109.5379638671875, 188.1142120361328, 127.6727294921875, 583.686279296875, 141.9002685546875, 270.62506103515625, 244.66346740722656, 257.29931640625, 206.35557556152344, 79.9642333984375, 134.4998321533203, 189.2292938232422, 256.3152160644531, 222.725341796875, 300.876953125, 275.4468994140625, 246.2811737060547, 81.63433074951172, 160.253662109375, 174.27403259277344, 147.4976348876953, 438.776123046875, 60.712158203125, 56.187255859375, 92.52685546875, 488.9736328125, 209.66566467285156, 169.33358764648438, 296.32574462890625, 322.59375, 104.65447235107422, 221.44158935546875, 417.175537109375, 73.97978210449219, 107.5316390991211, 375.55084228515625, 258.80084228515625, 237.0049591064453, 373.3821105957031, 151.48007202148438, 486.3583068847656, 207.24221801757812, 302.28912353515625, 225.52975463867188, 236.3148193359375, 173.6465606689453, 505.6019287109375, 188.64190673828125, 344.5294494628906, 143.1307373046875, 277.62451171875, 328.5754089355469, 451.8836975097656, 274.81756591796875, 368.0490417480469, 376.12451171875, 150.97840881347656, 175.4649200439453, 231.91064453125, 96.85487365722656, 304.37249755859375, 167.7970733642578, 465.1057434082031, 562.31982421875, 110.27587890625, 358.99749755859375, 280.07720947265625, 498.3701171875, 248.054443359375, 267.07489013671875, 271.837646484375, 177.96786499023438, 493.9498291015625, 450.1302490234375, 183.3455810546875, 185.8427734375, 344.5666198730469, 108.47531127929688, 427.8106994628906, 312.212646484375, 386.9149475097656, 123.09442138671875, 162.44790649414062, 73.23052215576172, 158.83984375, 140.66268920898438, 457.90673828125, 241.06358337402344, 108.206787109375, 142.03761291503906, 564.4231567382812, 229.04559326171875, 93.04457092285156, 403.431396484375, 265.59515380859375, 223.2572021484375, 176.314453125, 283.5412292480469, 499.0558166503906, 59.1163444519043, 213.00645446777344, 266.2330322265625, 399.6429748535156, 284.8478698730469, 86.56963348388672, 374.4637451171875, 346.8656311035156, 63.9325065612793, 509.8580627441406, 225.939208984375, 121.2392578125, 336.9256896972656, 337.5218200683594, 67.7918701171875, 619.1905517578125, 385.6612854003906, 443.1603088378906, 100.3787841796875, 120.77910614013672, 64.31853485107422, 347.1778869628906, 261.6215515136719, 239.912109375, 163.54759216308594, 614.0210571289062, 230.45330810546875, 98.12738037109375, 294.179443359375, 139.21246337890625, 209.88758850097656, 107.61997985839844, 321.85406494140625, 159.37606811523438, 110.5885009765625, 499.0448303222656, 92.94608306884766, 502.98138427734375, 255.35850524902344, 168.52587890625, 353.35028076171875, 522.0587158203125, 240.08538818359375, 60.8095703125, 354.6239013671875, 276.12554931640625, 184.10284423828125, 438.9483947753906, 425.12542724609375, 159.949462890625, 321.4896545410156, 79.413330078125, 138.378173828125, 291.4534606933594, 332.19873046875, 176.5498809814453, 533.6290283203125, 444.6128845214844, 285.05322265625, 468.6292724609375, 161.43272399902344, 184.4497833251953, 164.2430419921875, 440.36834716796875, 331.81536865234375, 198.92208862304688, 210.03651428222656, 214.9935302734375, 171.5458526611328, 226.12353515625, 492.4918518066406, 341.758544921875, 534.98388671875, 189.89111328125, 239.8079833984375, 551.602783203125, 205.1282958984375, 158.3709716796875, 127.2744140625, 58.73648452758789, 4.1901960372924805, 2.330998182296753, 2.380654811859131, 3.50920033454895, 2.9190967082977295, 1.846326231956482, 2.1927881240844727, 3.3665668964385986, 3.3653364181518555, 2.377469062805176, 2.919651508331299, 1.4053878784179688, 3.073925733566284, 2.2029688358306885, 2.2211267948150635, 3.238088846206665, 2.9346554279327393, 2.85829758644104, 2.255324363708496, 4.7666826248168945, 1.6669421195983887, 2.8820908069610596, 1.9531179666519165, 2.0393972396850586, 2.2917795181274414, 3.3900227546691895, 2.1946229934692383, 1.6938679218292236, 3.2546608448028564, 2.589794874191284, 2.249546527862549, 2.911716938018799, 1.8829888105392456, 3.2388904094696045, 2.42984676361084, 3.0135791301727295, 2.960047483444214, 2.9447717666625977, 2.025214195251465, 3.4576210975646973, 3.1577136516571045, 3.870448589324951, 2.050900459289551, 1.9202489852905273, 1.8913146257400513, 2.3598270416259766, 3.5895116329193115, 2.141906976699829, 3.4016435146331787, 2.387216091156006, 2.7413482666015625, 3.440617084503174, 3.1020500659942627, 1.716172456741333, 3.1849162578582764, 1.7370482683181763, 1.8804978132247925, 3.4824321269989014, 2.761744260787964, 3.5513429641723633, 2.8264381885528564, 3.2566709518432617, 3.1617236137390137, 1.9869354963302612, 2.7183258533477783, 2.680987596511841, 2.1563520431518555, 2.551083564758301, 2.832829713821411, 1.8165981769561768, 4.0359625816345215, 3.197272300720215, 2.8466460704803467, 1.4290761947631836, 3.965951681137085, 2.994915008544922, 3.062108039855957, 2.1135804653167725, 3.84283185005188, 2.7451393604278564, 2.9696123600006104, 3.7363121509552, 2.7518668174743652, 2.3005614280700684, 1.5779558420181274, 3.0052757263183594, 3.06524658203125, 2.0924291610717773, 2.0485754013061523, 2.3481435775756836, 3.555170774459839, 3.202709913253784, 2.1594858169555664, 2.0751256942749023, 2.376824378967285, 1.4568721055984497, 4.092648029327393, 3.211355447769165, 2.4294886589050293, 1.8432055711746216, 2.832139253616333, 2.578913450241089, 2.6968584060668945, 2.679154634475708, 2.9451165199279785, 2.4148051738739014, 2.408900737762451, 2.492539882659912, 3.077188014984131, 1.8450117111206055, 2.7058584690093994, 2.0720396041870117, 4.061379432678223, 2.180924415588379, 2.6592423915863037, 3.038111448287964, 2.547579765319824, 2.8539326190948486, 2.3448212146759033, 1.8527799844741821, 1.7355167865753174, 2.625339984893799, 2.820451259613037, 3.272773027420044, 2.248898506164551, 1.7074644565582275, 2.107548713684082, 2.875464677810669, 2.9051544666290283, 2.6835906505584717, 3.583348274230957, 2.2594194412231445, 2.626965284347534, 1.6931835412979126, 2.5138494968414307, 2.145280599594116, 3.1197588443756104, 1.8367046117782593, 3.04311466217041, 3.2499682903289795, 3.3964526653289795, 3.6494078636169434, 1.966292381286621, 3.4315712451934814, 4.463732719421387, 1.9312280416488647, 2.2503201961517334, 2.3078949451446533, 3.777630567550659, 2.4802350997924805, 1.803440809249878, 3.23034405708313, 2.1869821548461914, 2.460808277130127, 3.307199001312256, 3.1746227741241455, 2.773782253265381, 3.1981170177459717, 3.1298439502716064, 2.725705623626709, 2.9964091777801514, 3.7464370727539062, 2.5391111373901367, 3.540195941925049, 2.8293564319610596, 4.513642311096191, 2.580683469772339, 3.205151319503784, 2.834242820739746, 2.4624853134155273, 2.448481559753418, 2.1915884017944336, 2.583685874938965, 2.307642698287964, 4.012750148773193, 3.2504475116729736, 2.986786365509033, 3.1045334339141846, 3.2446746826171875, 2.5984814167022705, 1.6894140243530273, 2.6778857707977295, 2.411945104598999, 1.5358304977416992, 2.733264207839966, 1.8613817691802979, 1.655079960823059, 2.171556234359741, 2.897772789001465, 3.023209810256958, 3.09731125831604, 2.0319480895996094, 1.21731698513031, 2.6163442134857178, 2.9509923458099365, 2.851517915725708, 2.014160394668579, 2.2316904067993164, 3.4435112476348877, 2.837285280227661, 1.6878691911697388, 3.0165436267852783, 2.5088741779327393, 2.1594619750976562, 2.206416130065918, 2.3750855922698975, 3.068124294281006, 2.2576098442077637, 2.7082016468048096, 3.475372314453125, 2.0615310668945312, 2.2910397052764893, 2.215867280960083, 3.04435658454895, 2.4177582263946533, 3.6984004974365234, 2.739938974380493, 2.1319265365600586, 3.9304606914520264, 2.4016928672790527, 2.5855133533477783, 2.576159715652466, 3.4193115234375, 3.1794958114624023, 2.895615816116333, 1.3671674728393555, 3.525543212890625, 2.1766021251678467, 2.1793222427368164, 3.666142463684082, 2.208374261856079, 2.840571880340576, 2.5633468627929688, 2.8782989978790283, 2.4075675010681152, 2.636631488800049, 3.900256633758545, 2.421391487121582, 3.3547849655151367, 2.972977876663208, 2.8990068435668945, 3.1701366901397705, 2.880204916000366, 2.9029757976531982, 1.9393682479858398, 3.0394866466522217, 2.7344696521759033, 3.570526123046875, 3.679922342300415, 2.418177366256714, 3.047809362411499, 3.1507887840270996, 3.2068569660186768, 2.9389445781707764, 3.756343364715576, 2.17526912689209, 2.688784122467041, 1.806427001953125, 2.872344970703125, 1.9122234582901, 3.458435297012329, 2.622990608215332, 2.8192477226257324, 2.392705202102661, 3.4079582691192627, 1.9718905687332153, 3.302358865737915, 2.394357204437256, 1.7375695705413818, 3.7410571575164795, 3.3208720684051514, 2.9680747985839844, 1.9418706893920898, 2.749894380569458, 2.6986804008483887, 2.295539617538452, 2.8005950450897217, 3.6327507495880127, 2.8087053298950195, 2.048508882522583, 2.22208309173584, 2.8256046772003174, 2.101058006286621, 3.6687915325164795, 2.81033992767334, 2.614117383956909, 2.7188446521759033, 1.5882580280303955, 2.0980329513549805, 2.471414804458618, 2.0948803424835205, 3.376732349395752, 2.959975004196167, 3.3376338481903076, 3.3789117336273193, 1.933516502380371, 1.6567177772521973, 3.307713270187378, 2.74082088470459, 2.1636292934417725, 0.20596179366111755, 0.26864954829216003, 0.2465316653251648, 0.22627300024032593, 0.28937679529190063, 0.2983783781528473, 0.2571963965892792, 0.26892969012260437, 0.303724080324173, 0.25404396653175354, 0.2385835349559784, 0.2666693925857544, 0.20538121461868286, 0.18776923418045044, 0.33522966504096985, 0.3047013282775879, 0.21133896708488464, 0.25710389018058777, 0.21524997055530548, 0.32386261224746704, 0.28021788597106934, 0.30164697766304016, 0.26790761947631836, 0.255643367767334, 0.22552916407585144, 0.28733569383621216, 0.2810068428516388, 0.25906628370285034, 0.3150997459888458, 0.27004581689834595, 0.21435759961605072, 0.26967737078666687, 0.21737609803676605, 0.22417403757572174, 0.23618578910827637, 0.2662625014781952, 0.2888364791870117, 0.28961944580078125, 0.28693944215774536, 0.29230204224586487, 0.22275680303573608, 0.2967625856399536, 0.23857802152633667, 0.3085191547870636, 0.24513296782970428, 0.245131716132164, 0.24513667821884155, 0.25595054030418396, 0.31225496530532837, 0.26180002093315125, 0.24395549297332764, 0.33896979689598083, 0.20526859164237976, 0.2694566547870636, 0.2647837698459625, 0.23456692695617676, 0.2300788015127182, 0.27182647585868835, 0.2656518816947937, 0.2566520869731903, 0.2949804365634918, 0.26495811343193054, 0.27196550369262695, 0.21915218234062195, 0.2054254412651062, 0.32778915762901306, 0.27707478404045105, 0.2579251527786255, 0.283498615026474, 0.2685804069042206, 0.21727752685546875, 0.26278552412986755, 0.25457844138145447, 0.2457067370414734, 0.25334692001342773, 0.24059443175792694, 0.26231148838996887, 0.19730180501937866, 0.21948951482772827, 0.32850366830825806, 0.27758920192718506, 0.22060653567314148, 0.2111542969942093, 0.24518750607967377, 0.22941230237483978, 0.2701142728328705, 0.28271448612213135, 0.28045085072517395, 0.23805838823318481, 0.2628895342350006, 0.2740391790866852, 0.2758820950984955, 0.29465144872665405, 0.24110984802246094, 0.2238452434539795, 0.3043331503868103, 0.26004984974861145, 0.2633938789367676, 0.2995363473892212, 0.23101003468036652, 0.2676699459552765, 0.21594446897506714, 0.27300089597702026, 0.3007321357727051, 0.3010406494140625, 0.2859472930431366, 0.2274760752916336, 0.307461142539978, 0.272411048412323, 0.2725914418697357, 0.2909623980522156, 0.28010085225105286, 0.25862032175064087, 0.19759181141853333, 0.26186007261276245, 0.24735042452812195, 0.20785024762153625, 0.32570186257362366, 0.27456027269363403, 0.25312355160713196, 0.28473615646362305, 0.30794668197631836, 0.25335875153541565, 0.19870750606060028, 0.2174408733844757, 0.28036239743232727, 0.3053593337535858, 0.27609992027282715, 0.32647842168807983, 0.32979828119277954, 0.2970110774040222, 0.25488150119781494, 0.2600334882736206, 0.3113515079021454, 0.22455449402332306, 0.2613803446292877, 0.2381066083908081, 0.25965315103530884, 0.2709430158138275, 0.2522711455821991, 0.3253079950809479, 0.20319025218486786, 0.29853296279907227, 0.2836539149284363, 0.26556745171546936, 0.26788002252578735, 0.21182675659656525, 0.24518272280693054, 0.2524544894695282, 0.2262246459722519, 0.23623044788837433, 0.24056103825569153, 0.2826964855194092, 0.24517172574996948, 0.23242248594760895, 0.2706078290939331, 0.23620693385601044, 0.24063976109027863, 0.30044546723365784, 0.2290627658367157, 0.2272050380706787, 0.24914656579494476, 0.27413374185562134, 0.2950250506401062, 0.3092513084411621, 0.24567393958568573, 0.28322210907936096, 0.23896244168281555, 0.22856807708740234, 0.22356398403644562, 0.3050830364227295, 0.2316667139530182, 0.28299009799957275, 0.23920440673828125, 0.271970272064209, 0.26111602783203125, 0.21263286471366882, 0.263875275850296, 0.27847597002983093, 0.2987596392631531, 0.23322780430316925, 0.22909386456012726, 0.293269544839859, 0.2877883315086365, 0.33411550521850586, 0.2186974287033081, 0.2199147492647171, 0.2726558446884155, 0.17402461171150208, 0.2217576503753662, 0.2757975161075592, 0.32420921325683594, 0.2426261454820633, 0.2762957811355591, 0.27525657415390015, 0.3001328706741333, 0.22548362612724304, 0.2517990171909332, 0.30054226517677307, 0.27144744992256165, 0.21608275175094604, 0.2316443771123886, 0.3174065053462982, 0.26839786767959595, 0.2382931411266327, 0.2516905665397644, 0.30227920413017273, 0.25214883685112, 0.2489253580570221, 0.22859904170036316, 0.2546146810054779, 0.2731662392616272, 0.25508975982666016, 0.28000637888908386, 0.25389236211776733, 0.26707255840301514, 0.2449978142976761, 0.22694644331932068, 0.26751378178596497, 0.2821585536003113, 0.28497371077537537, 0.27029111981391907, 0.23201267421245575, 0.23344998061656952, 0.32425108551979065, 0.2208428680896759, 0.27618899941444397, 0.25236907601356506, 0.26063838601112366, 0.21830947697162628, 0.25864747166633606, 0.23969011008739471, 0.2839217782020569, 0.3826134502887726, 0.29116567969322205, 0.2350759506225586, 0.29249244928359985, 0.29595518112182617, 0.31147876381874084, 0.23394936323165894, 0.2646629512310028, 0.2909664213657379, 0.22418811917304993, 0.22797445952892303, 0.20980502665042877, 0.2592611014842987, 0.3009868860244751, 0.28244322538375854, 0.22574424743652344, 0.31937313079833984, 0.22943280637264252, 0.22338610887527466, 0.1845342069864273, 0.23902779817581177, 0.2730027735233307, 0.37440550327301025, 0.2567397356033325, 0.2559070587158203, 0.2276320457458496, 0.2875271141529083, 0.2209334373474121, 0.30103954672813416, 0.29140064120292664, 0.2954249382019043, 0.18492108583450317, 0.2826126515865326, 0.21500781178474426, 0.26997190713882446, 0.3079261779785156, 0.30010986328125, 0.25660350918769836, 0.22103863954544067, 0.22201405465602875, 0.2660171389579773, 0.26220834255218506, 0.212899312376976, 0.31401145458221436, 0.30837637186050415, 0.25797998905181885, 0.3187278211116791, 0.2902524173259735, 0.28083565831184387, 0.224858820438385, 0.30861446261405945, 0.19174034893512726, 0.281249076128006, 0.2833418846130371, 0.2383250743150711, 0.30471929907798767, 0.23778755962848663, 0.3142193555831909, 0.2781100273132324, 0.3035088777542114, 0.17818965017795563, 0.28186148405075073, 0.254976749420166, 0.24804356694221497, 0.22622673213481903, 0.24988782405853271, 0.30143922567367554, 4.7548370361328125, 3.181795597076416, 2.6186535358428955, 2.6034295558929443, 3.477964401245117, 3.0545952320098877, 3.522549867630005, 2.138812303543091, 4.052614212036133, 2.275538444519043, 2.7750630378723145, 3.131596565246582, 3.5921032428741455, 2.8835856914520264, 3.2598752975463867, 2.7527084350585938, 4.171319961547852, 3.345285177230835, 2.019347667694092, 3.383209705352783, 3.5901806354522705, 2.6888084411621094, 3.676607608795166, 3.206141948699951, 4.1177592277526855, 2.4144039154052734, 4.832456111907959, 3.5922820568084717, 4.3160905838012695, 2.6492083072662354, 3.7730259895324707, 2.0311174392700195, 2.6731462478637695, 3.241445541381836, 3.3611936569213867, 4.123469352722168, 3.114394426345825, 2.9957237243652344, 2.6960830688476562, 5.617866039276123, 4.149730205535889, 3.0490002632141113, 3.552185535430908, 3.460484266281128, 3.920078754425049, 2.450627326965332, 2.0427234172821045, 3.8293657302856445, 3.845402956008911, 4.162909030914307, 5.130014419555664, 4.140381336212158, 2.904528856277466, 2.813646078109741, 3.5220227241516113, 4.23392915725708, 2.1050634384155273, 2.935258150100708, 3.164297103881836, 3.312903881072998, 2.8505985736846924, 2.495814323425293, 2.973301649093628, 3.217672348022461, 4.3343610763549805, 3.822951078414917, 2.6010735034942627, 2.7025182247161865, 2.9130711555480957, 4.129003524780273, 2.4100210666656494, 3.213055372238159, 4.068711280822754, 4.15052604675293, 4.474324703216553, 4.08876371383667, 2.4454758167266846, 4.371976375579834, 4.955142498016357, 3.94451642036438, 3.2934234142303467, 4.440680980682373, 4.506155490875244, 2.312629461288452, 3.533838987350464, 2.377479076385498, 3.433655261993408, 3.7848339080810547, 3.315819263458252, 4.383067607879639, 3.075300931930542, 5.448009967803955, 2.4558143615722656, 3.4834790229797363, 2.8895299434661865, 2.9847328662872314, 3.5336833000183105, 4.329328536987305, 4.46248197555542, 3.7833142280578613, 3.506474018096924, 3.164503812789917, 4.558131694793701, 3.678013324737549, 3.9651172161102295, 2.2273330688476562, 4.524406433105469, 2.9817733764648438, 2.7809810638427734, 2.236102819442749, 3.2152225971221924, 2.48545241355896, 3.71928334236145, 3.546360969543457, 4.066659927368164, 2.7620837688446045, 3.732128143310547, 3.83642578125, 2.5894217491149902, 3.7486026287078857, 2.513594388961792, 2.7063229084014893, 4.059072494506836, 5.0809102058410645, 4.0358500480651855, 3.883455753326416, 3.3637325763702393, 3.153271436691284, 5.524653434753418, 4.111825942993164, 2.7063839435577393, 2.9247710704803467, 3.5806667804718018, 3.5331475734710693, 2.5979838371276855, 2.4051473140716553, 2.5332705974578857, 3.8741137981414795, 3.8905041217803955, 4.3314313888549805, 4.841798782348633, 2.196979284286499, 3.98333477973938, 2.8191044330596924, 2.6128625869750977, 4.18055534362793, 3.3390026092529297, 3.4865128993988037, 3.5617833137512207, 4.35787296295166, 2.582326889038086, 3.2870659828186035, 2.4053032398223877, 4.197216510772705, 3.1232120990753174, 2.8251609802246094, 2.538754940032959, 3.3969032764434814, 2.7217705249786377, 2.668915271759033, 2.4544262886047363, 2.6083884239196777, 2.3784303665161133, 3.6166141033172607, 2.8092546463012695, 2.671212911605835, 4.06096076965332, 3.055006742477417, 4.1719794273376465, 4.204072952270508, 2.233157157897949, 4.10003662109375, 2.6100430488586426, 4.1764984130859375, 3.9275994300842285, 2.8853771686553955, 2.5795464515686035, 3.689795732498169, 3.750183582305908, 2.150357246398926, 4.029513359069824, 2.683664083480835, 4.607741832733154, 4.127750873565674, 5.171292781829834, 3.538914680480957, 3.447301149368286, 2.6417300701141357, 3.1137402057647705, 3.542078733444214, 3.0866611003875732, 3.4936153888702393, 3.4902806282043457, 4.863533020019531, 5.229775428771973, 5.3231706619262695, 2.4398977756500244, 3.538844108581543, 3.1720733642578125, 4.563047409057617, 5.232254981994629, 4.0143938064575195, 2.964869976043701, 3.3589446544647217, 3.9729180335998535, 5.454736232757568, 4.223230838775635, 4.403838634490967, 3.323765754699707, 4.077817440032959, 4.589569091796875, 5.537728786468506, 2.7091362476348877, 3.9033470153808594, 4.025967121124268, 2.980536699295044, 3.6821811199188232, 4.59356689453125, 2.0800251960754395, 2.445357084274292, 2.666687488555908, 2.2605600357055664, 5.083597183227539, 3.731034994125366, 3.7766804695129395, 4.085430145263672, 2.997974157333374, 2.5391764640808105, 3.88600754737854, 2.9294345378875732, 2.720616102218628, 3.8226940631866455, 3.462982177734375, 2.320702075958252, 2.5713438987731934, 3.7189559936523438, 2.8911943435668945, 3.1213884353637695, 3.936058521270752, 3.7402026653289795, 3.015839099884033, 3.202101469039917, 3.4088945388793945, 4.003305435180664, 3.7976765632629395, 4.336579322814941, 4.346932411193848, 3.010068893432617, 3.3335447311401367, 4.434391975402832, 2.8859996795654297, 3.3053600788116455, 4.580727577209473, 3.84611439704895, 4.40298318862915, 3.6785619258880615, 2.914292573928833, 3.8376598358154297, 2.4038126468658447, 3.0635690689086914, 3.3012120723724365, 3.91899037361145, 4.169855117797852, 3.348393678665161, 2.187408208847046, 3.40624737739563, 3.4363579750061035, 2.3465826511383057, 2.108553886413574, 3.95111083984375, 2.595733642578125, 4.155585765838623, 4.019895076751709, 2.7588424682617188, 3.82085919380188, 2.7294909954071045, 2.335819721221924, 2.7474453449249268, 3.2095887660980225, 3.005549669265747, 3.9516727924346924, 4.641662120819092, 6.004316806793213, 3.9512546062469482, 3.479192018508911, 4.4855780601501465, 3.773085832595825, 2.5455589294433594, 4.163254737854004, 3.6555051803588867, 3.0161502361297607, 3.7929022312164307, 3.4539546966552734, 2.2916617393493652, 2.785219669342041, 4.231481552124023, 3.931765556335449, 3.8760509490966797, 2.7352516651153564, 4.25478458404541, 515.5572509765625, 38.68072509765625, 90.78450012207031, 201.9920196533203, 223.97483825683594, 231.30140686035156, 271.26318359375, 529.3670043945312, 140.226806640625, 390.16900634765625, 258.33331298828125, 72.1798095703125, 76.6077880859375, 503.109375, 239.82843017578125, 191.7822265625, 188.8695831298828, 269.9570617675781, 632.4985961914062, 424.2269287109375, 496.9855651855469, 270.28076171875, 305.7990417480469, 530.4236450195312, 203.73497009277344, 116.897705078125, 170.48757934570312, 109.12680053710938, 260.9051513671875, 403.908203125, 137.152099609375, 315.4244384765625, 226.682373046875, 116.62054443359375, 84.60365295410156, 142.242919921875, 224.00889587402344, 52.041748046875, 320.705078125, 94.11876678466797, 212.725341796875, 204.04946899414062, 143.82379150390625, 453.8154296875, 184.42921447753906, 68.23128509521484, 239.66845703125, 95.7151870727539, 429.6875, 502.3690490722656, 256.5830078125, 318.17913818359375, 279.1080322265625, 467.834716796875, 522.377685546875, 385.19189453125, 452.6872863769531, 64.052001953125, 156.24549865722656, 296.59429931640625, 278.15771484375, 324.9854736328125, 374.9820251464844, 131.28240966796875, 354.1047058105469, 109.83511352539062, 279.65692138671875, 356.5553283691406, 212.88763427734375, 246.80784606933594, 157.34759521484375, 261.64263916015625, 299.88690185546875, 67.18354034423828, 152.9804229736328, 262.7296447753906, 450.155029296875, 126.69671630859375, 568.8970947265625, 406.595703125, 251.64804077148438, 161.6703338623047, 251.03538513183594, 193.1691436767578, 288.0887451171875, 330.8029479980469, 122.92290496826172, 379.3971862792969, 105.74683380126953, 100.64945983886719, 297.5686340332031, 200.9196319580078, 160.0189666748047, 349.80242919921875, 294.3713684082031, 169.3093719482422, 278.757568359375, 509.9847412109375, 476.7887268066406, 343.658203125, 218.9521484375, 112.5062255859375, 391.672607421875, 300.7912292480469, 471.96685791015625, 77.42718505859375, 214.833740234375, 77.172607421875, 323.0888671875, 395.85650634765625, 249.7367706298828, 280.7591552734375, 148.31155395507812, 272.7751770019531, 381.2225646972656, 99.2523193359375, 272.4481506347656, 580.0159912109375, 179.8333740234375, 260.8142395019531, 63.8079833984375, 365.3080139160156, 53.11888122558594, 242.29730224609375, 293.2489318847656, 203.83018493652344, 176.7451934814453, 580.0055541992188, 116.1990966796875, 214.26971435546875, 68.84575653076172, 219.433349609375, 354.48492431640625, 105.84954833984375, 195.99205017089844, 403.08740234375, 182.73460388183594, 229.59922790527344, 337.98828125, 233.90740966796875, 223.78285217285156, 78.40558624267578, 291.857421875, 278.64080810546875, 76.0853271484375, 310.910888671875, 202.9140167236328, 244.66123962402344, 429.6544494628906, 115.765869140625, 172.81494140625, 326.92578125, 245.95147705078125, 414.08819580078125, 310.833740234375, 303.40863037109375, 337.5637512207031, 140.63897705078125, 342.04656982421875, 59.58367919921875, 430.5389099121094, 324.4864501953125, 78.6822509765625, 116.547119140625, 110.12511444091797, 226.6981658935547, 213.9080047607422, 324.017578125, 167.30108642578125, 422.2853088378906, 218.4046630859375, 275.8029479980469, 213.13916015625, 170.2894287109375, 139.82325744628906, 281.0824890136719, 526.2555541992188, 133.33680725097656, 222.3993377685547, 76.1392822265625, 85.74271392822266, 230.07334899902344, 168.5541229248047, 249.78575134277344, 38.5501708984375, 617.70849609375, 130.29551696777344, 169.36911010742188, 112.55682373046875, 262.9684143066406, 326.5451354980469, 85.92790985107422, 273.696044921875, 204.5562286376953, 251.5185089111328, 323.99755859375, 207.6448974609375, 384.5390625, 246.7407684326172, 490.41656494140625, 254.799560546875, 283.14678955078125, 160.81689453125, 257.1759948730469, 112.57266998291016, 318.072265625, 167.99154663085938, 198.11767578125, 84.2892837524414, 303.8644714355469, 113.8740234375, 387.9646911621094, 136.49034118652344, 229.69091796875, 277.73968505859375, 228.858642578125, 265.4618225097656, 455.8257751464844, 207.9545135498047, 107.82820129394531, 245.0048828125, 85.39178466796875, 344.5643310546875, 216.2117919921875, 634.7159423828125, 83.87067413330078, 346.923828125, 669.5557861328125, 72.15478515625, 375.8402404785156, 399.4660339355469, 183.0074005126953, 225.9842529296875, 291.6151123046875, 234.74554443359375, 447.7610168457031, 520.7274780273438, 133.52151489257812, 244.2357940673828, 64.08587646484375, 194.82839965820312, 168.198974609375, 244.91162109375, 298.7591247558594, 84.07241821289062, 282.0724792480469, 117.07343292236328, 214.076904296875, 93.26569366455078, 437.3644714355469, 465.2657775878906, 367.6419982910156, 207.87762451171875, 117.11602020263672, 141.48211669921875, 260.2952880859375, 276.94891357421875, 344.5724792480469, 509.9317932128906, 246.47216796875, 228.87950134277344, 478.864013671875, 394.5245361328125, 179.992919921875, 232.454833984375, 365.0909729003906, 212.4939422607422, 104.6358871459961, 220.1024169921875, 95.85614013671875, 338.9542236328125, 263.443115234375, 214.38282775878906, 193.16270446777344, 465.9518737792969, 171.4530029296875, 488.599365234375, 344.5201416015625, 221.18875122070312, 125.70293426513672, 411.4299011230469, 622.3677978515625, 73.803466796875, 274.7814636230469, 415.3355407714844, 279.6304931640625, 115.477294921875, 251.07742309570312, 155.28436279296875, 87.13664245605469, 104.86322021484375, 433.3810119628906, 84.72468566894531, 229.64718627929688, 315.0242614746094, 171.8065948486328, 185.7133026123047, 194.0536651611328, 112.47708892822266, 240.07620239257812, 2.4463112354278564, 3.3845348358154297, 3.6388773918151855, 2.348742723464966, 2.7745301723480225, 3.2059741020202637, 2.789496421813965, 3.68510365486145, 2.8926708698272705, 2.3376173973083496, 2.2749319076538086, 2.763697385787964, 1.944358468055725, 4.340932369232178, 3.1864891052246094, 2.272019386291504, 2.448648691177368, 3.76344895362854, 2.7754452228546143, 2.241793632507324, 2.3156957626342773, 1.662636637687683, 1.8161165714263916, 3.3394060134887695, 1.5720380544662476, 1.6001195907592773, 2.875786781311035, 3.2392327785491943, 2.1016130447387695, 1.6907049417495728, 3.5443780422210693, 1.9792171716690063, 3.0289146900177, 3.7413084506988525, 2.6517670154571533, 1.8512969017028809, 1.637373924255371, 2.281877279281616, 3.367070198059082, 3.4780821800231934, 1.6736810207366943, 3.6829729080200195, 1.9684276580810547, 2.849229097366333, 3.401336193084717, 3.7073333263397217, 1.9709959030151367, 3.1752514839172363, 2.8250973224639893, 2.3502557277679443, 2.6644198894500732, 2.3801207542419434, 2.5501739978790283, 3.908655881881714, 2.3288588523864746, 1.2089524269104004, 3.4251010417938232, 1.9125945568084717, 3.1883490085601807, 2.072108268737793, 2.501596689224243, 3.0879149436950684, 1.6877869367599487, 2.624865770339966, 2.881287097930908, 2.6324315071105957, 2.5019619464874268, 2.571650743484497, 2.011608839035034, 1.7648277282714844, 1.5333051681518555, 2.543882369995117, 1.8244560956954956, 3.0476841926574707, 2.864354133605957, 1.9195564985275269, 3.5573511123657227, 2.906304359436035, 3.105860471725464, 1.884139060974121, 2.813807964324951, 2.110854148864746, 3.277132987976074, 4.182816505432129, 3.061826705932617, 2.6662700176239014, 4.0082902908325195, 2.534688949584961, 2.236088752746582, 2.107853889465332, 1.825595498085022, 1.9083738327026367, 2.911757230758667, 2.1370368003845215, 2.2911410331726074, 3.0250139236450195, 1.900246500968933, 1.5299711227416992, 1.9949603080749512, 2.024228096008301, 1.7444167137145996, 3.2355241775512695, 2.6679699420928955, 3.0196926593780518, 1.3821868896484375, 2.2360124588012695, 2.2253737449645996, 2.4485299587249756, 2.0282771587371826, 3.2020504474639893, 1.3737554550170898, 2.158909559249878, 3.024707794189453, 2.6441116333007812, 2.67050838470459, 1.930201530456543, 1.6398611068725586, 2.4167137145996094, 2.0863492488861084, 2.165452003479004, 3.7674779891967773, 2.8331151008605957, 2.555238962173462, 3.0314018726348877, 2.579188585281372, 3.8215532302856445, 3.378298759460449, 2.390233039855957, 2.8088505268096924, 2.1480417251586914, 2.4285287857055664, 2.686782121658325, 2.5449612140655518, 1.8249273300170898, 1.9034347534179688, 3.738156318664551, 1.9650461673736572, 2.1255102157592773, 2.3305470943450928, 1.8358449935913086, 2.2282495498657227, 2.517916679382324, 1.8274940252304077, 2.2462973594665527, 1.4701262712478638, 2.496415615081787, 2.233748197555542, 2.9787724018096924, 2.6372179985046387, 2.0148518085479736, 2.9697258472442627, 2.46820068359375, 3.432216167449951, 3.6236844062805176, 2.629380464553833, 2.7670738697052, 2.261590003967285, 2.893341064453125, 2.406977891921997, 2.860461473464966, 1.5393379926681519, 2.515177011489868, 3.1365480422973633, 2.6266374588012695, 3.1613235473632812, 2.6726653575897217, 3.5763158798217773, 2.2294092178344727, 1.6653436422348022, 3.3841443061828613, 3.6075994968414307, 2.214229106903076, 1.919066071510315, 2.9457333087921143, 2.466905117034912, 2.396573066711426, 3.107910394668579, 2.643857479095459, 1.3673679828643799, 2.8085110187530518, 1.7162590026855469, 2.2458267211914062, 3.4039125442504883, 1.939510464668274, 2.30947208404541, 1.9600969552993774, 2.733718156814575, 2.377068519592285, 3.0160176753997803, 2.2566542625427246, 2.148108720779419, 2.3425588607788086, 2.3203954696655273, 3.295335292816162, 2.5505475997924805, 2.071319580078125, 2.615992307662964, 3.262009859085083, 2.172684669494629, 2.1894006729125977, 1.726088523864746, 2.7028441429138184, 4.054434776306152, 2.6170766353607178, 1.7499771118164062, 1.935685396194458, 1.999310851097107, 2.3540115356445312, 1.5864286422729492, 1.3176648616790771, 2.5331056118011475, 3.2106828689575195, 2.69016170501709, 1.9662636518478394, 2.520341396331787, 2.659452438354492, 2.8336095809936523, 2.785994291305542, 2.5046205520629883, 2.937211275100708, 3.5503528118133545, 1.9150466918945312, 2.725717306137085, 3.5183117389678955, 3.3255703449249268, 2.3859243392944336, 2.309081792831421, 3.3018980026245117, 3.7594707012176514, 2.6980090141296387, 2.8878467082977295, 2.7759294509887695, 3.534459352493286, 2.927720546722412, 3.1059558391571045, 3.9284234046936035, 2.6844589710235596, 2.460020065307617, 2.4155657291412354, 1.6959658861160278, 3.682040214538574, 2.046253204345703, 2.46037220954895, 2.773887872695923, 2.2449750900268555, 1.6299718618392944, 3.0490758419036865, 2.352351665496826, 2.50203800201416, 2.941758394241333, 1.7497320175170898, 2.1836037635803223, 1.9693853855133057, 2.4759411811828613, 1.5375512838363647, 2.4275200366973877, 2.781146287918091, 3.2508838176727295, 1.6341081857681274, 2.2995173931121826, 2.901801109313965, 3.994516134262085, 3.0258495807647705, 3.126847505569458, 3.0227763652801514, 2.6548149585723877, 2.2395029067993164, 1.7343847751617432, 3.2625889778137207, 3.1222643852233887, 1.7525910139083862, 2.099177360534668, 1.5186179876327515, 2.6914660930633545, 2.042973041534424, 2.8352627754211426, 3.7148373126983643, 2.4620485305786133, 3.27178955078125, 2.091221809387207, 1.4765480756759644, 2.1490392684936523, 3.3841240406036377, 2.3475656509399414, 3.372042655944824, 2.7012834548950195, 1.938448190689087, 1.7110483646392822, 3.1402924060821533, 2.1277763843536377, 4.09814453125, 2.80887508392334, 3.8193676471710205, 2.20278263092041, 2.940272808074951, 1.4780826568603516, 1.8143295049667358, 2.4493844509124756, 3.160710334777832, 3.926121711730957, 0.20294509828090668, 0.24675039947032928, 0.2823110818862915, 0.2955096662044525, 0.2593926191329956, 0.23277422785758972, 0.2615346610546112, 0.25103703141212463, 0.28738728165626526, 0.27275213599205017, 0.2499370127916336, 0.23437197506427765, 0.28634539246559143, 0.2198578268289566, 0.24688224494457245, 0.33228799700737, 0.2405243217945099, 0.308460533618927, 0.28889065980911255, 0.2828425467014313, 0.21862943470478058, 0.22665052115917206, 0.3336406946182251, 0.2606603801250458, 0.2602253556251526, 0.29616332054138184, 0.2873191833496094, 0.24028457701206207, 0.27023863792419434, 0.2585867643356323, 0.2592729926109314, 0.33880525827407837, 0.2183661162853241, 0.291201114654541, 0.2286207377910614, 0.2671085000038147, 0.22662895917892456, 0.25489234924316406, 0.29431572556495667, 0.26664045453071594, 0.27380505204200745, 0.22324053943157196, 0.1861393004655838, 0.25849267840385437, 0.22362510859966278, 0.3012125790119171, 0.27887991070747375, 0.24164867401123047, 0.20153723657131195, 0.19448725879192352, 0.2425648272037506, 0.21404705941677094, 0.2642422914505005, 0.22324666380882263, 0.29967159032821655, 0.2309737354516983, 0.26201772689819336, 0.27355217933654785, 0.2629467248916626, 0.24202559888362885, 0.28033921122550964, 0.3033170700073242, 0.2575426697731018, 0.2686586380004883, 0.30760490894317627, 0.26937803626060486, 0.15739774703979492, 0.2943827509880066, 0.2119140774011612, 0.24101622402668, 0.26190322637557983, 0.2705845534801483, 0.28423866629600525, 0.22215983271598816, 0.23043374717235565, 0.26588520407676697, 0.25103259086608887, 0.29088225960731506, 0.2913951873779297, 0.25393834710121155, 0.28247353434562683, 0.27512672543525696, 0.28447577357292175, 0.30051106214523315, 0.3123505413532257, 0.24583163857460022, 0.3133077621459961, 0.3190511167049408, 0.24827037751674652, 0.28128865361213684, 0.2574922740459442, 0.2308053970336914, 0.3120058476924896, 0.24486343562602997, 0.29489943385124207, 0.303256094455719, 0.2708457410335541, 0.2472495585680008, 0.262005090713501, 0.24344481527805328, 0.28438737988471985, 0.26636621356010437, 0.2816072404384613, 0.2883678078651428, 0.23659753799438477, 0.27561336755752563, 0.3060949146747589, 0.333783358335495, 0.2325693517923355, 0.32819464802742004, 0.21320275962352753, 0.2743375599384308, 0.2779777944087982, 0.34026938676834106, 0.30126625299453735, 0.2539086937904358, 0.3206581473350525, 0.259551465511322, 0.25151345133781433, 0.2902193069458008, 0.2343342900276184, 0.2573051452636719, 0.22924120724201202, 0.24740804731845856, 0.26071107387542725, 0.2966899275779724, 0.31536865234375, 0.2949846088886261, 0.22534257173538208, 0.31985920667648315, 0.2586272656917572, 0.23593857884407043, 0.24644820392131805, 0.24057208001613617, 0.269785612821579, 0.2541004717350006, 0.2693575918674469, 0.3486240804195404, 0.26125314831733704, 0.2531532347202301, 0.2769753634929657, 0.2717031240463257, 0.21989750862121582, 0.24502918124198914, 0.17411410808563232, 0.274748295545578, 0.31878772377967834, 0.22566431760787964, 0.2366843968629837, 0.22088146209716797, 0.2771762013435364, 0.23482295870780945, 0.2162940949201584, 0.26895180344581604, 0.2174488753080368, 0.28543365001678467, 0.2935892343521118, 0.28235024213790894, 0.21471518278121948, 0.23889735341072083, 0.256137877702713, 0.20687636733055115, 0.28221020102500916, 0.3349418640136719, 0.2785004675388336, 0.20185275375843048, 0.2697809934616089, 0.2746719419956207, 0.20289547741413116, 0.2811865210533142, 0.30192700028419495, 0.2894201874732971, 0.27536848187446594, 0.19308269023895264, 0.22779811918735504, 0.2556951940059662, 0.19511988759040833, 0.33980104327201843, 0.24949407577514648, 0.2921135127544403, 0.3115972876548767, 0.28824150562286377, 0.24643981456756592, 0.19049552083015442, 0.24547767639160156, 0.3070801794528961, 0.24493305385112762, 0.24556593596935272, 0.30672329664230347, 0.23164355754852295, 0.2036173939704895, 0.29011985659599304, 0.20441791415214539, 0.2417459785938263, 0.24923263490200043, 0.21341575682163239, 0.2809267044067383, 0.30480343103408813, 0.25745779275894165, 0.29105520248413086, 0.21794076263904572, 0.33721938729286194, 0.2872926592826843, 0.3043217062950134, 0.2130541354417801, 0.2668044865131378, 0.27750182151794434, 0.2876307964324951, 0.2714217007160187, 0.2493150681257248, 0.22011621296405792, 0.2555406093597412, 0.2486790418624878, 0.2629512548446655, 0.2399105429649353, 0.23467619717121124, 0.2964286208152771, 0.3160460889339447, 0.23803134262561798, 0.28966110944747925, 0.22492384910583496, 0.29606616497039795, 0.24775487184524536, 0.20586687326431274, 0.27757561206817627, 0.22676368057727814, 0.3145766258239746, 0.26549938321113586, 0.3132735788822174, 0.30248430371284485, 0.24049337208271027, 0.23539435863494873, 0.20646579563617706, 0.22881385684013367, 0.26101139187812805, 0.311217725276947, 0.2720867097377777, 0.28967735171318054, 0.2717891335487366, 0.3037470877170563, 0.2319076508283615, 0.29672202467918396, 0.2345384955406189, 0.22624237835407257, 0.28878897428512573, 0.25359010696411133, 0.2746371328830719, 0.29050275683403015, 0.2606319487094879, 0.28333574533462524, 0.2556082308292389, 0.2960265576839447, 0.2821040749549866, 0.28151920437812805, 0.2052587866783142, 0.29200980067253113, 0.24890105426311493, 0.24773208796977997, 0.2643825113773346, 0.2773224711418152, 0.28199487924575806, 0.3285413384437561, 0.3068244755268097, 0.35495415329933167, 0.21211592853069305, 0.21510723233222961, 0.30366581678390503, 0.26612213253974915, 0.24715934693813324, 0.31652000546455383, 0.25998562574386597, 0.29958686232566833, 0.25381872057914734, 0.23022586107254028, 0.32172927260398865, 0.18294070661067963, 0.3382375240325928, 0.26285287737846375, 0.2307490110397339, 0.26240435242652893, 0.29818227887153625, 0.24776959419250488, 0.28566473722457886, 0.26383814215660095, 0.2016056329011917, 0.24570544064044952, 0.25664183497428894, 0.21011601388454437, 0.26992130279541016, 0.2341955155134201, 0.21519874036312103, 0.3139674961566925, 0.2927597463130951, 0.32880789041519165, 0.27564218640327454, 0.2610750198364258, 0.2520286440849304, 0.2137763500213623, 0.24229483306407928, 0.2850501239299774, 2.091413974761963, 4.415599346160889, 3.436110258102417, 3.417236804962158, 4.2049384117126465, 6.144018650054932, 3.7941606044769287, 3.308624744415283, 3.412158727645874, 3.879366874694824, 2.2478346824645996, 2.2604920864105225, 3.426577091217041, 3.6017956733703613, 3.920074462890625, 3.2669568061828613, 3.743549108505249, 3.8000149726867676, 5.549660682678223, 4.181088924407959, 3.209866762161255, 4.907990455627441, 2.5663363933563232, 4.7117486000061035, 2.663478374481201, 3.416163921356201, 3.4475162029266357, 3.772352933883667, 3.986114978790283, 2.263688802719116, 4.633783340454102, 4.210152626037598, 2.994391441345215, 3.687584638595581, 2.745931625366211, 3.535451650619507, 3.9273457527160645, 2.5821661949157715, 2.9798641204833984, 4.830157279968262, 3.436133623123169, 5.250064373016357, 3.5804219245910645, 2.372034788131714, 4.453296184539795, 3.2151577472686768, 2.963695526123047, 2.8321850299835205, 2.847759962081909, 2.2282605171203613, 3.841215133666992, 4.366689682006836, 3.1145312786102295, 2.986463785171509, 2.69242262840271, 3.5868711471557617, 3.809713363647461, 4.2478437423706055, 3.9948577880859375, 2.9755382537841797, 3.2904858589172363, 4.7365288734436035, 3.8946807384490967, 3.450263500213623, 3.8447635173797607, 4.921095371246338, 2.810425281524658, 2.421306610107422, 4.078582286834717, 4.0472893714904785, 2.440953016281128, 4.4886651039123535, 2.3849682807922363, 5.509221076965332, 3.327846050262451, 3.88139271736145, 3.990081787109375, 4.367477893829346, 4.918590545654297, 2.378249168395996, 3.26776123046875, 2.3482799530029297, 3.615593910217285, 4.764759540557861, 3.7452075481414795, 2.8350536823272705, 4.109745979309082, 4.182917594909668, 3.0692341327667236, 2.078809976577759, 3.168773651123047, 4.001328468322754, 3.5557408332824707, 3.9424045085906982, 3.601163148880005, 4.1778693199157715, 3.791051149368286, 4.075954914093018, 3.989109516143799, 3.462815523147583, 3.8601348400115967, 4.0432844161987305, 2.6492533683776855, 3.950732946395874, 3.387723922729492, 5.474969387054443, 3.068955659866333, 3.2451188564300537, 4.402373790740967, 2.870823383331299, 2.7744860649108887, 2.955308198928833, 5.214883804321289, 2.591228485107422, 3.300542116165161, 2.7273998260498047, 3.167858839035034, 3.2922275066375732, 3.6686065196990967, 2.412792205810547, 4.789535999298096, 2.626782178878784, 3.9413578510284424, 4.0715012550354, 4.766046524047852, 3.7934391498565674, 3.552628755569458, 4.214770793914795, 3.9645602703094482, 3.7936620712280273, 2.6476423740386963, 4.083927631378174, 2.0992469787597656, 3.7282445430755615, 4.622199058532715, 2.4376211166381836, 2.724534034729004, 3.902773857116699, 4.00123405456543, 3.7451870441436768, 2.544949531555176, 4.235995292663574, 4.099812984466553, 2.7965691089630127, 3.1408188343048096, 3.159883975982666, 2.8657543659210205, 4.098186492919922, 3.3632805347442627, 4.335272312164307, 6.0677618980407715, 4.107515335083008, 4.137867450714111, 3.008059024810791, 2.446950674057007, 2.8264050483703613, 3.048325777053833, 4.985748291015625, 3.991896390914917, 2.037900447845459, 1.939387321472168, 4.835744380950928, 3.51175594329834, 2.6626574993133545, 2.305894374847412, 4.175103187561035, 4.343812942504883, 3.207941770553589, 3.3094241619110107, 2.8993852138519287, 4.361763000488281, 3.443026542663574, 3.810499906539917, 3.135847806930542, 2.90765380859375, 2.44970965385437, 2.9181718826293945, 4.528870582580566, 4.057509899139404, 4.543737888336182, 2.377880096435547, 3.865753650665283, 2.926480531692505, 3.382603168487549, 2.862093448638916, 3.2957849502563477, 3.363905668258667, 2.892608642578125, 2.9117372035980225, 3.0136444568634033, 3.112097978591919, 3.4973397254943848, 3.7259433269500732, 4.331148624420166, 2.8299267292022705, 3.3633244037628174, 3.967985153198242, 3.8023736476898193, 4.356114864349365, 2.0287954807281494, 3.455594301223755, 4.914712905883789, 3.594980001449585, 2.4852235317230225, 2.1616461277008057, 3.1403744220733643, 2.6851489543914795, 3.1127758026123047, 3.696458578109741, 2.463595151901245, 4.1226701736450195, 3.096946954727173, 3.4886956214904785, 5.275052547454834, 2.86694073677063, 3.0999882221221924, 3.0867233276367188, 3.4786369800567627, 2.2068631649017334, 3.6598401069641113, 3.9620120525360107, 5.059812068939209, 5.000632286071777, 2.940514087677002, 3.412428617477417, 4.0606160163879395, 2.728397846221924, 5.584660530090332, 5.923099040985107, 2.4977149963378906, 4.444551467895508, 2.6231584548950195, 5.779398441314697, 3.772874116897583, 3.38793683052063, 4.089502334594727, 2.9848363399505615, 3.689311981201172, 2.346278429031372, 3.0342190265655518, 3.142000675201416, 3.8147976398468018, 5.158389568328857, 3.196049928665161, 3.9375088214874268, 4.072170734405518, 3.0810909271240234, 2.7770330905914307, 3.569899320602417, 4.038050651550293, 2.702604293823242, 3.3074822425842285, 5.171432971954346, 2.604822874069214, 3.0490849018096924, 4.784336566925049, 3.4515023231506348, 2.662559986114502, 4.3595356941223145, 4.650934219360352, 2.5735414028167725, 2.4708645343780518, 3.896177291870117, 3.1561596393585205, 2.249051094055176, 2.673588752746582, 4.213992118835449, 2.377854824066162, 3.2635293006896973, 3.114253282546997, 4.085170745849609, 3.0404961109161377, 2.816976547241211, 3.4045121669769287, 3.326127767562866, 3.756411075592041, 3.006883382797241, 3.210779905319214, 3.6847381591796875, 3.234680652618408, 3.0679595470428467, 3.9672458171844482, 3.732347249984741, 3.21909499168396, 3.7786271572113037, 3.2592613697052, 3.4547441005706787, 4.531985282897949, 2.1824796199798584, 2.1520256996154785, 2.4848949909210205, 1.8123207092285156, 4.513079643249512, 3.7105424404144287, 3.738375663757324, 2.4017584323883057, 4.38092565536499, 3.2963757514953613, 4.265779972076416, 3.573683977127075, 485.19677734375, 648.5626220703125, 121.10997772216797, 250.0222930908203, 268.4259033203125, 296.9617919921875, 119.6778793334961, 605.135009765625, 187.35757446289062, 375.1486511230469, 185.6136474609375, 263.6605529785156, 167.36338806152344, 234.1025390625, 155.82601928710938, 398.4855041503906, 365.7681884765625, 392.55694580078125, 348.06451416015625, 136.87864685058594, 326.483154296875, 532.7718505859375, 293.87945556640625, 196.3060302734375, 609.0008544921875, 406.8727111816406, 151.60821533203125, 171.99522399902344, 518.2616577148438, 241.3157958984375, 320.36285400390625, 129.43663024902344, 348.0184631347656, 97.8173828125, 309.80419921875, 140.38502502441406, 674.9595336914062, 550.4374389648438, 138.48468017578125, 91.43931579589844, 607.614501953125, 100.52373504638672, 223.25457763671875, 131.2938232421875, 247.26483154296875, 77.25172424316406, 66.0291748046875, 42.53433609008789, 208.57289123535156, 156.6582794189453, 247.970947265625, 377.01202392578125, 78.31898498535156, 153.07334899902344, 155.83837890625, 71.8768310546875, 496.6028747558594, 140.65200805664062, 159.09307861328125, 113.530029296875, 179.45713806152344, 531.116455078125, 145.7428741455078, 197.51817321777344, 499.15625, 101.43077850341797, 344.78765869140625, 348.1366271972656, 245.9539337158203, 188.71417236328125, 126.6448974609375, 154.7534942626953, 410.4105224609375, 75.458740234375, 397.1636962890625, 430.13616943359375, 258.4089660644531, 265.98638916015625, 496.1759338378906, 181.2939453125, 137.57830810546875, 222.48114013671875, 506.310546875, 289.3573303222656, 369.4459228515625, 82.88751983642578, 197.6651153564453, 298.6268615722656, 570.125, 211.0443115234375, 479.7569274902344, 535.1737670898438, 180.83889770507812, 268.5663757324219, 329.57122802734375, 82.70344543457031, 741.6309814453125, 629.6796875, 358.9644470214844, 400.9364318847656, 235.7505340576172, 177.18344116210938, 297.6583251953125, 148.78565979003906, 348.6185607910156, 253.09417724609375, 256.3511962890625, 123.50785064697266, 419.86273193359375, 250.5454559326172, 210.3789825439453, 436.8641662597656, 123.1579818725586, 253.2328643798828, 145.7914276123047, 270.6964111328125, 181.11241149902344, 219.3270721435547, 133.85411071777344, 136.54351806640625, 210.00418090820312, 607.5944213867188, 258.8013916015625, 164.68772888183594, 265.94158935546875, 72.09280395507812, 348.0675048828125, 184.5254669189453, 215.06016540527344, 312.43701171875, 238.300537109375, 228.47998046875, 105.094970703125, 198.9753875732422, 254.37841796875, 366.0045166015625, 279.865478515625, 345.7677917480469, 287.86456298828125, 470.94659423828125, 92.60565185546875, 189.86798095703125, 504.3482666015625, 163.181884765625, 191.1082763671875, 191.1601104736328, 263.32562255859375, 271.14886474609375, 186.69781494140625, 107.27825927734375, 230.4930419921875, 85.7919921875, 445.4337463378906, 212.67149353027344, 430.23565673828125, 101.91775512695312, 249.269775390625, 186.5693359375, 206.43968200683594, 527.3968505859375, 103.20892333984375, 375.038818359375, 76.15087890625, 398.09906005859375, 358.6279296875, 150.60565185546875, 492.1695861816406, 216.68948364257812, 210.5332794189453, 154.87559509277344, 506.6156005859375, 122.19296264648438, 132.2869873046875, 363.1126403808594, 339.62451171875, 322.5130615234375, 68.1983642578125, 308.9198303222656, 311.4049072265625, 139.510986328125, 148.87539672851562, 467.3863830566406, 228.755126953125, 222.66644287109375, 144.19775390625, 653.6643676757812, 385.014404296875, 375.8155822753906, 229.9228515625, 199.0519561767578, 515.0696411132812, 400.6034240722656, 229.6201934814453, 71.6969985961914, 83.27996063232422, 203.9248046875, 247.7073974609375, 398.8365783691406, 108.9872055053711, 58.101318359375, 362.5731506347656, 275.0025634765625, 217.22039794921875, 379.8790588378906, 257.193359375, 298.2413330078125, 493.9774475097656, 268.51287841796875, 67.9578857421875, 226.12136840820312, 139.7420654296875, 420.1285095214844, 208.66064453125, 711.1043701171875, 251.14491271972656, 406.7109375, 331.47265625, 326.60516357421875, 356.7783508300781, 292.7813720703125, 327.447998046875, 226.9521484375, 147.8612060546875, 252.0546417236328, 347.5304260253906, 404.0217590332031, 172.81210327148438, 156.8956756591797, 425.1028137207031, 262.9403076171875, 556.238037109375, 85.978759765625, 288.4248046875, 196.3514404296875, 301.2352294921875, 434.549560546875, 651.072509765625, 660.7177734375, 81.83840942382812, 578.425048828125, 235.2715606689453, 576.474365234375, 139.96798706054688, 285.2365417480469, 291.8182373046875, 154.68756103515625, 160.0267791748047, 177.0452880859375, 518.2904052734375, 187.85675048828125, 616.3868408203125, 101.12218475341797, 79.89710235595703, 451.7135314941406, 305.12603759765625, 306.768310546875, 425.6922912597656, 205.27752685546875, 217.8803253173828, 501.7696838378906, 96.1502685546875, 339.05975341796875, 305.29937744140625, 98.64935302734375, 458.3656005859375, 131.4005126953125, 230.78330993652344, 430.1257629394531, 134.87010192871094, 398.43853759765625, 400.1556701660156, 358.924560546875, 524.5146484375, 121.6810302734375, 182.02728271484375, 118.22901153564453, 348.5137023925781, 64.9991455078125, 112.55986785888672, 373.01513671875, 108.313720703125, 89.93167114257812, 306.9294738769531, 166.0501708984375, 231.49807739257812, 193.8827667236328, 349.64227294921875, 645.720947265625, 450.725341796875, 253.34475708007812, 171.394287109375, 449.906005859375, 367.4521484375, 122.1031494140625, 517.2164916992188, 216.82241821289062, 704.9910278320312, 592.2086791992188, 341.88427734375, 56.312801361083984, 3.8267087936401367, 2.508897066116333, 3.286602735519409, 3.613661766052246, 3.4483439922332764, 2.9161577224731445, 2.3847780227661133, 2.4584147930145264, 1.8989325761795044, 2.6400952339172363, 2.3795363903045654, 2.7663071155548096, 2.3345346450805664, 2.5031988620758057, 4.08901309967041, 1.8269647359848022, 3.2321395874023438, 2.151238441467285, 1.5007718801498413, 2.329995632171631, 3.9350156784057617, 2.0267865657806396, 2.8652007579803467, 2.6807658672332764, 3.2868669033050537, 1.6343168020248413, 3.358466625213623, 2.0663444995880127, 2.6781322956085205, 2.5367801189422607, 1.6757562160491943, 1.6207685470581055, 3.6436665058135986, 3.3409178256988525, 1.932277798652649, 2.042881965637207, 3.113337278366089, 3.0415666103363037, 2.0911519527435303, 1.8590651750564575, 3.336050033569336, 2.3142406940460205, 1.8599789142608643, 1.9153857231140137, 3.2070412635803223, 2.6604092121124268, 3.4242358207702637, 1.6493253707885742, 2.583261013031006, 1.2196063995361328, 2.688493013381958, 1.957850456237793, 4.0894012451171875, 2.2157909870147705, 2.45864200592041, 2.4931745529174805, 1.781825065612793, 2.3513402938842773, 3.434300661087036, 3.418952226638794, 3.643547773361206, 2.9473912715911865, 1.5976766347885132, 1.9112768173217773, 2.2503957748413086, 1.6922472715377808, 3.7370007038116455, 1.9083107709884644, 2.41855525970459, 2.656590461730957, 2.4968860149383545, 3.242825508117676, 3.3124172687530518, 2.759652614593506, 3.4790966510772705, 2.518571615219116, 1.8830369710922241, 2.734532356262207, 2.197063446044922, 2.5927226543426514, 2.3109962940216064, 2.4804015159606934, 3.6633899211883545, 1.7107266187667847, 3.1680595874786377, 1.975113034248352, 3.066765785217285, 3.348215341567993, 3.430629253387451, 1.6322784423828125, 2.879018783569336, 3.073124647140503, 3.0619399547576904, 3.5277833938598633, 1.8468636274337769, 2.1638174057006836, 3.5020573139190674, 2.108505964279175, 1.6669020652770996, 3.143738269805908, 1.9911537170410156, 2.3915507793426514, 3.8471972942352295, 2.2383339405059814, 2.083836555480957, 2.45760440826416, 2.775599718093872, 1.933638572692871, 3.0633533000946045, 3.2998857498168945, 4.1002020835876465, 1.168343186378479, 1.8171662092208862, 2.5690410137176514, 3.0125858783721924, 1.9633721113204956, 3.4603679180145264, 1.071097493171692, 3.4526329040527344, 2.078399896621704, 1.3110321760177612, 2.639019727706909, 3.015730619430542, 2.601641893386841, 3.1257107257843018, 3.053518295288086, 2.007784843444824, 2.8366692066192627, 2.4560914039611816, 4.109335899353027, 4.059935092926025, 2.3799619674682617, 3.120488166809082, 2.215426445007324, 3.2315244674682617, 2.499957323074341, 2.06833553314209, 2.4123857021331787, 1.8189122676849365, 4.252106666564941, 3.684983968734741, 2.263547420501709, 2.450474739074707, 2.053652763366699, 3.5162017345428467, 2.4900755882263184, 2.8718478679656982, 2.94084095954895, 2.9530274868011475, 2.10537052154541, 3.1436102390289307, 2.0399227142333984, 3.1249020099639893, 3.1078178882598877, 2.5836143493652344, 3.5894744396209717, 2.943621873855591, 3.54107403755188, 3.2507216930389404, 1.8104668855667114, 2.857029914855957, 1.725067138671875, 2.6497771739959717, 2.1121485233306885, 2.5959112644195557, 3.136298418045044, 2.9532830715179443, 3.011547803878784, 3.753040313720703, 3.680126905441284, 3.34464168548584, 2.2819747924804688, 2.427762031555176, 2.7389583587646484, 3.7721972465515137, 2.9908056259155273, 3.4872448444366455, 3.207540273666382, 3.350419282913208, 2.565211772918701, 3.5869860649108887, 2.3347673416137695, 3.783230781555176, 2.084548234939575, 1.8525495529174805, 2.6253764629364014, 3.720562696456909, 2.8061535358428955, 2.5707733631134033, 1.900288462638855, 3.54531192779541, 2.6487855911254883, 3.4494988918304443, 4.050596714019775, 1.9915075302124023, 3.561551332473755, 2.698789119720459, 1.7538824081420898, 2.9325342178344727, 2.275876522064209, 2.719792366027832, 1.844399333000183, 2.1154263019561768, 3.429202079772949, 1.8216980695724487, 1.995103120803833, 2.806389093399048, 3.2091245651245117, 3.0469932556152344, 2.083376884460449, 3.0855624675750732, 2.402115821838379, 2.731397867202759, 1.64229154586792, 3.6419613361358643, 2.7332751750946045, 2.708796739578247, 3.6598734855651855, 2.3896729946136475, 2.0450706481933594, 2.3760604858398438, 4.116347789764404, 4.308121681213379, 3.79044246673584, 2.4577760696411133, 2.06215238571167, 1.7115468978881836, 3.343518018722534, 1.9167094230651855, 2.2809505462646484, 2.6890478134155273, 3.4545183181762695, 2.0743515491485596, 3.291987419128418, 3.2903099060058594, 2.4002106189727783, 2.2719345092773438, 2.0772829055786133, 2.9680206775665283, 2.6589136123657227, 3.6767566204071045, 2.309250831604004, 2.3955605030059814, 3.6997880935668945, 1.9486397504806519, 2.789680004119873, 3.316983461380005, 3.197603940963745, 3.82646107673645, 2.481106758117676, 2.1711339950561523, 3.1334822177886963, 2.5479555130004883, 2.6516149044036865, 2.36519718170166, 2.2978744506835938, 2.0865719318389893, 3.2924983501434326, 2.391066551208496, 3.5617024898529053, 2.2999770641326904, 2.715101957321167, 3.1028759479522705, 2.9732143878936768, 2.863037586212158, 3.5808937549591064, 2.93673038482666, 2.393449068069458, 1.5734871625900269, 2.2914953231811523, 1.900141716003418, 1.4972882270812988, 3.1115634441375732, 2.1488146781921387, 2.72860050201416, 3.216864824295044, 1.0886402130126953, 4.067286968231201, 2.4252443313598633, 1.5356606245040894, 2.2809135913848877, 3.6932859420776367, 2.640826463699341, 3.0487377643585205, 3.4487907886505127, 3.6606719493865967, 3.169252872467041, 3.2347402572631836, 4.154868125915527, 4.0303144454956055, 2.994279146194458, 3.865718364715576, 2.3311281204223633, 3.4963200092315674, 2.4852800369262695, 2.676224946975708, 2.5975613594055176, 3.981201648712158, 2.4245266914367676, 2.0890073776245117, 0.2130439132452011, 0.27715784311294556, 0.31249794363975525, 0.28817763924598694, 0.27662208676338196, 0.29335349798202515, 0.2768561840057373, 0.2133883237838745, 0.31470730900764465, 0.25152015686035156, 0.20257721841335297, 0.2995166778564453, 0.3163830637931824, 0.29283344745635986, 0.3485027849674225, 0.2999705672264099, 0.315166175365448, 0.2822001874446869, 0.22325082123279572, 0.28578174114227295, 0.32844218611717224, 0.3238891661167145, 0.297368586063385, 0.20921416580677032, 0.21250180900096893, 0.2705285847187042, 0.2566889226436615, 0.2591210901737213, 0.2767150104045868, 0.32998937368392944, 0.24241413176059723, 0.2276630699634552, 0.2794843912124634, 0.24946869909763336, 0.3285052180290222, 0.28795942664146423, 0.24379019439220428, 0.24780681729316711, 0.3378576636314392, 0.23457972705364227, 0.24159635603427887, 0.2394132912158966, 0.29977697134017944, 0.3019885718822479, 0.26450613141059875, 0.3170906901359558, 0.22635357081890106, 0.2594985067844391, 0.21716918051242828, 0.21987766027450562, 0.24585986137390137, 0.2807568311691284, 0.28412216901779175, 0.23377029597759247, 0.240446537733078, 0.26134204864501953, 0.2302936315536499, 0.2245873361825943, 0.20284345746040344, 0.2078937292098999, 0.28512799739837646, 0.25622978806495667, 0.1925411969423294, 0.22343502938747406, 0.2521283030509949, 0.22360864281654358, 0.26704177260398865, 0.24934066832065582, 0.21107028424739838, 0.30845504999160767, 0.25608476996421814, 0.3063836991786957, 0.27948811650276184, 0.324695885181427, 0.24976637959480286, 0.2157861590385437, 0.2347806841135025, 0.30780157446861267, 0.21666502952575684, 0.27081993222236633, 0.21498841047286987, 0.2567858099937439, 0.23216529190540314, 0.21595627069473267, 0.30436357855796814, 0.23836137354373932, 0.2579755485057831, 0.29725325107574463, 0.28376516699790955, 0.168079674243927, 0.28345343470573425, 0.23537135124206543, 0.21126967668533325, 0.2630004584789276, 0.29101598262786865, 0.2729015350341797, 0.2761724293231964, 0.2730666995048523, 0.23726573586463928, 0.24331621825695038, 0.2552814483642578, 0.23970812559127808, 0.2564942240715027, 0.30596479773521423, 0.2552579343318939, 0.238687664270401, 0.27419087290763855, 0.32754427194595337, 0.2625826895236969, 0.2996201515197754, 0.27208438515663147, 0.25315728783607483, 0.22684195637702942, 0.22067692875862122, 0.23647315800189972, 0.2723284959793091, 0.21085700392723083, 0.2495918571949005, 0.28516796231269836, 0.23868678510189056, 0.2667650878429413, 0.2736101448535919, 0.27682363986968994, 0.2552195191383362, 0.3034111261367798, 0.26883089542388916, 0.255615234375, 0.25526973605155945, 0.32463425397872925, 0.30959904193878174, 0.33213263750076294, 0.28439220786094666, 0.20574122667312622, 0.29653534293174744, 0.31819459795951843, 0.2776778042316437, 0.3388456702232361, 0.32155841588974, 0.31585168838500977, 0.244785338640213, 0.23193590342998505, 0.26300910115242004, 0.27398067712783813, 0.24752292037010193, 0.2326476275920868, 0.23987047374248505, 0.27954331040382385, 0.2851007580757141, 0.2623256742954254, 0.27266937494277954, 0.24107681214809418, 0.21747885644435883, 0.25209152698516846, 0.2524730861186981, 0.23205116391181946, 0.23381808400154114, 0.2848515808582306, 0.28351372480392456, 0.29863956570625305, 0.3288820683956146, 0.3118206262588501, 0.26177749037742615, 0.23513269424438477, 0.18519268929958344, 0.2569190561771393, 0.2443133443593979, 0.2784130275249481, 0.26328393816947937, 0.34925562143325806, 0.22170497477054596, 0.2696972191333771, 0.26580575108528137, 0.26757097244262695, 0.22552205622196198, 0.3534083366394043, 0.21018356084823608, 0.3470732271671295, 0.2914089858531952, 0.3059695065021515, 0.2645428478717804, 0.28018367290496826, 0.31938135623931885, 0.30267685651779175, 0.2901906669139862, 0.24098920822143555, 0.23882484436035156, 0.22910578548908234, 0.23646274209022522, 0.3013269007205963, 0.26568603515625, 0.2235465794801712, 0.3146499991416931, 0.2710418701171875, 0.24778898060321808, 0.22649918496608734, 0.2671387195587158, 0.21757932007312775, 0.2866211235523224, 0.27308109402656555, 0.24678155779838562, 0.2659717798233032, 0.2375403493642807, 0.23847465217113495, 0.2603309154510498, 0.24442648887634277, 0.30074113607406616, 0.29063719511032104, 0.21918419003486633, 0.34735479950904846, 0.23716086149215698, 0.27609387040138245, 0.2542858421802521, 0.24787795543670654, 0.28815171122550964, 0.26395729184150696, 0.2226676344871521, 0.327719122171402, 0.23731395602226257, 0.2371969223022461, 0.26534774899482727, 0.22021842002868652, 0.33154913783073425, 0.23617413640022278, 0.21506153047084808, 0.30266544222831726, 0.26865270733833313, 0.3163314461708069, 0.33304205536842346, 0.24575331807136536, 0.2875640392303467, 0.26991528272628784, 0.26539137959480286, 0.29998424649238586, 0.25563064217567444, 0.3317001163959503, 0.2829338610172272, 0.3254394829273224, 0.2616056799888611, 0.2165476232767105, 0.30544543266296387, 0.2674446403980255, 0.23729141056537628, 0.2736993432044983, 0.29370102286338806, 0.2790290415287018, 0.20462800562381744, 0.28953996300697327, 0.29964479804039, 0.2542155385017395, 0.2323520928621292, 0.309765487909317, 0.2495022565126419, 0.293203204870224, 0.3055257797241211, 0.30952179431915283, 0.34277278184890747, 0.24025122821331024, 0.285260945558548, 0.30753093957901, 0.17804567515850067, 0.2786270081996918, 0.26587820053100586, 0.21836444735527039, 0.22729645669460297, 0.24684534966945648, 0.3110894560813904, 0.2468344271183014, 0.23239608108997345, 0.30094993114471436, 0.30227428674697876, 0.2573668360710144, 0.26050612330436707, 0.3096441626548767, 0.3067157566547394, 0.28273913264274597, 0.22438709437847137, 0.23185820877552032, 0.25981125235557556, 0.2566780745983124, 0.2667294144630432, 0.21863196790218353, 0.31643256545066833, 0.2669336199760437, 0.20743823051452637, 0.3382115960121155, 0.22898104786872864, 0.26165124773979187, 0.32012739777565, 0.2046421766281128, 0.22068122029304504, 0.29222801327705383, 0.32259809970855713, 0.25051817297935486, 0.22133111953735352, 0.2415400594472885, 0.2739464044570923, 0.24664068222045898, 0.25463545322418213, 0.23109592497348785, 0.2543121576309204, 2.957658052444458, 2.4407873153686523, 4.85484504699707, 4.424404144287109, 3.8688511848449707, 2.202552080154419, 4.205848217010498, 3.7102959156036377, 2.9516918659210205, 2.470860004425049, 3.723754405975342, 2.9079060554504395, 2.5758111476898193, 3.399372100830078, 4.064063549041748, 2.9144749641418457, 3.4372761249542236, 3.318938732147217, 3.0822112560272217, 4.599003791809082, 3.3905563354492188, 2.433370590209961, 3.940664291381836, 3.1643712520599365, 4.192981243133545, 2.4485795497894287, 5.579355239868164, 3.794698715209961, 3.3840832710266113, 2.4282872676849365, 2.9162323474884033, 2.8771684169769287, 3.6263976097106934, 4.005887985229492, 2.0922768115997314, 4.115655422210693, 4.80850887298584, 2.2868869304656982, 3.554215669631958, 2.439894676208496, 3.6968934535980225, 4.62042760848999, 2.964134454727173, 5.068612098693848, 2.7290401458740234, 4.031727313995361, 3.3218648433685303, 2.575906991958618, 3.7431557178497314, 4.195908546447754, 3.3636066913604736, 3.8601372241973877, 3.9504170417785645, 3.1352832317352295, 2.5728721618652344, 2.3859219551086426, 3.67291259765625, 5.029155731201172, 3.879002332687378, 5.378660678863525, 3.6770739555358887, 3.0127251148223877, 2.124833822250366, 2.3153610229492188, 2.9608190059661865, 2.905060291290283, 5.201865196228027, 2.66323184967041, 2.7842724323272705, 3.50174617767334, 3.933636426925659, 3.208803653717041, 2.453947067260742, 3.3805947303771973, 2.6208653450012207, 2.7741305828094482, 3.2471089363098145, 2.746515989303589, 3.9840824604034424, 4.396829128265381, 4.808165073394775, 2.8984947204589844, 3.3913819789886475, 4.076526165008545, 3.0113589763641357, 3.731494665145874, 3.077761173248291, 3.302706718444824, 2.8413760662078857, 4.967031002044678, 3.827428102493286, 2.733363628387451, 5.738366603851318, 3.1969704627990723, 3.418802499771118, 2.8599853515625, 4.00035285949707, 5.201635837554932, 3.8517537117004395, 3.9596753120422363, 3.3511838912963867, 3.2371585369110107, 4.900501728057861, 3.350952625274658, 1.9364254474639893, 2.41111421585083, 3.293856620788574, 5.333818435668945, 4.04532527923584, 3.6579132080078125, 2.5508623123168945, 2.915362596511841, 3.9589195251464844, 3.0878429412841797, 4.404793739318848, 3.237030029296875, 3.941206693649292, 3.06097149848938, 4.253558158874512, 3.355320453643799, 2.3319146633148193, 2.855499744415283, 3.627164125442505, 3.5980751514434814, 4.726007461547852, 2.734245777130127, 3.20060658454895, 3.213691234588623, 3.457744598388672, 5.592281341552734, 2.801456928253174, 3.6849923133850098, 2.771739959716797, 2.8568239212036133, 2.6072287559509277, 4.178805828094482, 3.079287052154541, 4.148589611053467, 3.093318462371826, 4.5713791847229, 4.007218360900879, 4.208880424499512, 3.6985390186309814, 3.5418922901153564, 3.9521167278289795, 3.4131977558135986, 2.8135592937469482, 4.23824405670166, 4.734152793884277, 2.65103816986084, 3.255042314529419, 2.7523751258850098, 3.161038637161255, 3.076561450958252, 5.113710403442383, 3.2989718914031982, 2.974935293197632, 2.9258334636688232, 3.9384922981262207, 2.97668194770813, 2.5078353881835938, 2.8990161418914795, 2.8241424560546875, 3.5867509841918945, 3.580831289291382, 3.953643798828125, 3.1067631244659424, 4.637752056121826, 3.441103458404541, 4.404786586761475, 4.760928630828857, 2.4063589572906494, 4.539791584014893, 3.7660698890686035, 2.8617029190063477, 3.205310583114624, 3.058551073074341, 2.6303062438964844, 5.404732704162598, 3.02937912940979, 3.363285779953003, 3.5845916271209717, 4.613517761230469, 1.9870314598083496, 5.267534255981445, 4.892366886138916, 5.745189666748047, 3.3472700119018555, 2.7736146450042725, 3.379634380340576, 2.1730878353118896, 3.8568291664123535, 2.8279247283935547, 4.280130386352539, 3.83886456489563, 4.351238250732422, 2.781651020050049, 4.322145462036133, 3.200385570526123, 3.6484897136688232, 4.51093864440918, 3.113234281539917, 3.9540462493896484, 4.859133720397949, 3.35680890083313, 3.2827579975128174, 3.1033618450164795, 5.777443885803223, 2.6115028858184814, 3.9156723022460938, 2.4023277759552, 4.719377517700195, 3.8938679695129395, 5.028632164001465, 2.5672922134399414, 3.006387233734131, 2.2795515060424805, 3.3771419525146484, 2.8108978271484375, 3.1020219326019287, 4.593696594238281, 2.9827651977539062, 3.69963002204895, 3.380605697631836, 4.505556583404541, 2.7539525032043457, 3.3075757026672363, 3.3862011432647705, 3.334200382232666, 2.654367208480835, 4.352808952331543, 3.4350621700286865, 2.06870174407959, 3.575791597366333, 3.5412309169769287, 3.4311447143554688, 2.999054431915283, 3.1587975025177, 4.5619049072265625, 4.398745536804199, 4.382960319519043, 4.577478885650635, 3.273851156234741, 3.734795093536377, 3.3689863681793213, 3.324244976043701, 2.7084603309631348, 3.530050277709961, 2.8732211589813232, 3.659360885620117, 4.221391677856445, 3.7047066688537598, 2.6004979610443115, 3.599174976348877, 2.7498767375946045, 2.2154059410095215, 3.3017168045043945, 3.0521786212921143, 3.2626094818115234, 3.41019606590271, 4.880818843841553, 4.001646518707275, 2.53482723236084, 3.9097366333007812, 3.871091842651367, 3.5137510299682617, 4.585031509399414, 3.9655184745788574, 3.753826856613159, 3.3011157512664795, 2.8353874683380127, 2.5695390701293945, 3.3096842765808105, 4.564837455749512, 4.4711785316467285, 3.7455968856811523, 4.4873504638671875, 5.279929161071777, 2.9027745723724365, 3.5693395137786865, 2.7803239822387695, 3.285717010498047, 4.741517066955566, 3.4392271041870117, 2.5475552082061768, 2.6095082759857178, 3.2797253131866455, 4.861103057861328, 3.372950553894043, 2.5878167152404785, 2.9621663093566895, 2.3245277404785156, 3.2884013652801514, 2.8078973293304443, 3.52474308013916, 3.209226608276367, 2.9249162673950195, 3.869440793991089, 2.1796340942382812, 3.3846001625061035, 181.92860412597656, 218.13218688964844, 183.30081176757812, 179.4490966796875, 405.9210205078125, 295.3228759765625, 258.2892761230469, 174.6571807861328, 221.014404296875, 332.5461120605469, 96.7710952758789, 243.7422637939453, 155.8437042236328, 86.98460388183594, 237.35438537597656, 485.4903869628906, 239.0849609375, 546.9952392578125, 277.657958984375, 284.67144775390625, 210.79052734375, 182.8317413330078, 411.6876525878906, 92.52215576171875, 367.0476989746094, 321.2510986328125, 151.8218536376953, 158.24380493164062, 234.46194458007812, 204.2601318359375, 173.96929931640625, 224.82679748535156, 454.7611083984375, 185.8684539794922, 103.58294677734375, 137.48472595214844, 364.1061096191406, 558.8935546875, 418.8365478515625, 348.1942443847656, 324.7195129394531, 326.38275146484375, 306.98577880859375, 180.8656768798828, 241.59405517578125, 203.8056182861328, 98.99669647216797, 359.3233947753906, 105.7655029296875, 80.119384765625, 186.68858337402344, 135.73876953125, 751.456298828125, 499.08349609375, 241.0476531982422, 301.481201171875, 231.03445434570312, 262.1347961425781, 575.4144287109375, 433.3193359375, 125.28466796875, 551.3397827148438, 242.79052734375, 385.5244140625, 104.96405792236328, 79.17144012451172, 264.8341979980469, 187.77972412109375, 287.5047302246094, 247.32937622070312, 264.55926513671875, 272.75537109375, 145.58062744140625, 239.99624633789062, 455.26861572265625, 121.36264038085938, 406.748779296875, 51.88575744628906, 417.8958740234375, 407.723388671875, 134.62200927734375, 459.9452209472656, 736.7195434570312, 162.91824340820312, 304.5989074707031, 368.34405517578125, 272.9420166015625, 668.7407836914062, 65.80067443847656, 157.83607482910156, 350.61883544921875, 157.04656982421875, 90.6317138671875, 340.89593505859375, 297.29058837890625, 473.8399963378906, 443.2864990234375, 368.4459228515625, 451.30999755859375, 568.491943359375, 355.4820861816406, 345.5978698730469, 1006.4825439453125, 80.93560028076172, 121.21245574951172, 105.987548828125, 290.5301513671875, 181.58750915527344, 116.61830139160156, 234.048828125, 223.6580352783203, 104.82061004638672, 97.53418731689453, 362.76422119140625, 394.44921875, 274.0470275878906, 323.8492431640625, 162.80751037597656, 288.8330383300781, 497.17523193359375, 427.5887451171875, 231.416748046875, 96.53363037109375, 464.41259765625, 209.57960510253906, 676.8079833984375, 160.97967529296875, 52.2646484375, 324.1691589355469, 524.873046875, 197.13623046875, 131.4231719970703, 411.2176818847656, 104.0472640991211, 307.1418151855469, 382.6961364746094, 131.913818359375, 138.1496124267578, 108.01954650878906, 262.9381103515625, 336.2119140625, 646.6204833984375, 71.34425354003906, 59.330692291259766, 279.74444580078125, 152.77305603027344, 50.93157958984375, 208.7015380859375, 224.0984649658203, 232.50897216796875, 338.98779296875, 240.38047790527344, 443.6913146972656, 455.0615234375, 356.9205322265625, 459.6915588378906, 80.32880401611328, 426.1075744628906, 60.72492980957031, 199.0125732421875, 83.28815460205078, 793.4265747070312, 389.7545166015625, 260.186279296875, 285.9813232421875, 365.21728515625, 80.404541015625, 193.70703125, 75.57230377197266, 209.7445526123047, 260.5867919921875, 478.0072021484375, 327.90838623046875, 85.55660247802734, 243.2196044921875, 59.76868438720703, 490.66461181640625, 226.07530212402344, 465.2418518066406, 122.79656982421875, 215.43408203125, 206.2470703125, 633.556640625, 247.1702880859375, 223.6301727294922, 287.5698547363281, 537.4273071289062, 270.2685546875, 270.5693664550781, 272.6109619140625, 502.61834716796875, 174.02685546875, 183.35655212402344, 118.9356918334961, 215.9261016845703, 93.29991912841797, 265.56109619140625, 219.0418701171875, 316.5390625, 256.4330749511719, 152.21142578125, 83.17243957519531, 295.90948486328125, 433.4149475097656, 193.9064483642578, 279.69012451171875, 325.7900390625, 123.94646453857422, 134.79815673828125, 483.6962890625, 497.4939880371094, 190.40830993652344, 359.4945983886719, 329.3973083496094, 322.87060546875, 109.30620574951172, 436.3993225097656, 104.3612060546875, 666.8135986328125, 391.88531494140625, 406.4925842285156, 208.16371154785156, 118.51402282714844, 178.2353057861328, 192.59222412109375, 140.6220703125, 423.0685119628906, 274.2507629394531, 348.15380859375, 279.84246826171875, 206.7987823486328, 473.1939697265625, 537.764404296875, 86.99636840820312, 462.4270324707031, 180.92315673828125, 184.0214385986328, 488.0870666503906, 620.5794067382812, 202.86260986328125, 169.09825134277344, 240.7021484375, 291.2186279296875, 216.31182861328125, 280.5926513671875, 397.3536682128906, 98.35645294189453, 260.2178955078125, 117.4792709350586, 192.5174560546875, 51.852020263671875, 51.608367919921875, 468.8446350097656, 222.6179962158203, 261.2022705078125, 504.0218505859375, 252.07191467285156, 129.284423828125, 856.2490234375, 69.5628662109375, 198.40444946289062, 352.5089111328125, 93.505615234375, 179.69097900390625, 652.1500854492188, 197.04795837402344, 72.7977523803711, 171.5791778564453, 110.5595703125, 262.0306396484375, 271.2355041503906, 495.1525573730469, 190.78948974609375, 450.99639892578125, 298.9683837890625, 370.5955505371094, 200.5140380859375, 186.42930603027344, 291.0748291015625, 77.72145080566406, 399.21783447265625, 544.6904296875, 59.118709564208984, 186.2578887939453, 763.3468627929688, 108.56401824951172, 270.65557861328125, 210.8133544921875, 368.04644775390625, 144.89892578125, 371.4752197265625, 703.1598510742188, 99.64080810546875, 328.3387756347656, 296.114013671875, 174.65968322753906, 138.87664794921875, 65.89161682128906, 344.6107482910156, 248.02175903320312]
Average loss across all functions: 29.7408
Total runtime: 26087.73 seconds
